# Homework 3 Solutions

BEE 4850/5850

## Overview

### Instructions

The goal of this homework assignment is to practice developing and
working with probability models for data.

-   Problem 1 asks you to quantify uncertainties for a simple model
    using Bayesian statistics and rejection sampling.
-   Problem 2 asks you to use Monte Carlo simulation to calculate annual
    expected flooding damages.
-   Problem 3 (only required for students in BEE 5850) asks you to
    conduct cost-benefit analyses of housing elevation levels under
    future flooding uncertainty using Monte Carlo simulations.

### Load Environment

The following code loads the environment and makes sure all needed
packages are installed. This should be at the start of most Julia
scripts.

In [1]:
import Pkg
Pkg.activate(@__DIR__)
Pkg.instantiate()

The following packages are included in the environment (to help you find
other similar packages in other languages). The code below loads these
packages for use in the subsequent notebook (the desired functionality
for each package is commented next to the package).

In [1]:
using Random # random number generation and seed-setting
using DataFrames # tabular data structure
using CSV # reads/writes .csv files
using Distributions # interface to work with probability distributions
using Plots # plotting library
using StatsBase # statistical quantities like mean, median, etc
using StatsPlots # some additional statistical plotting tools
using Optim # optimization tools

Random.seed!(500)

## Problems

### Scoring

-   Problem 1 is worth 13 points.
-   Problem 2 is worth 7 points.
-   Problem 3 is worth 5 points.

### Problem 1

The probability model for the cheating responses is based on a Binomial
distribution, which reflects the number of successes (“yes” responses in
this case) in $n$ trials with probability $p$. What is the probability
of getting a “yes”? This can happen in two ways. First, with probability
$0.5$, the student gets a heads in the first toss and answers honestly,
which means they will answer “yes” with probability $\theta$. Otherwise,
they flip the coin again and answer “yes” if the coin comes up heads, an
outcome which occurs with probability 0.25. So the probability of a
“yes” is $p=0.5\theta + 0.25$. Therefore, the probability model is:

$$
\begin{aligned}
y &\sim Binomial(100, 0.5\theta + 0.25) \\
\theta &\sim \Beta(3, 40).
\end{aligned}
$$

Now we can use a grid approximation to compute and visualize the
posterior given the data of 31 “yes” answers. We will still do our
calculations on the log scale to avoid issues with numerical underflow,
even though we will plot the posterior on the density scale to help our
rejection sampling.

In [1]:
lprior(θ) = logpdf(Beta(3, 40), θ)
llikelihood(θ, y) = logpdf(Binomial(100, 0.5 * θ + 0.25), y)
lposterior(θ, y) = lprior(θ) + llikelihood(θ, y)

θ = 0:0.005:1
lp = lposterior.(θ, 40)
plot(θ, exp.(lp))

To draw samples with rejection sampling, we have a few options. As we
can see from
<a href="#fig-p1-posterior" class="quarto-xref">Figure 1</a>, the
density is bounded from above by 0.03, so we can use simple uniform
rejection sampling. This will likely not be very efficient since the
posterior is close to zero along most of the unit interval. However,
it’s relatively straightforward, so we’ll just use it.

In [1]:
post_samples = zeros(1_000)
# we will use a counter to keep count of how many samples we've kept
kept_samples = 0
while kept_samples < 1_000
    # generate a proposal
    x = rand(Uniform(0, 1))
    u = rand(Uniform(0, 1))
    if 0.03 * u < exp(lposterior(x, 40))
        kept_samples += 1
        post_samples[kept_samples] = x
    end
end

histogram(post_samples, label=false, xlabel="θ", ylabel="Count")

Comparing <a href="#fig-p1-samples" class="quarto-xref">Figure 2</a> to
<a href="#fig-p1-posterior" class="quarto-xref">Figure 1</a>, the
distributions look similar. So we don’t need more samples, though it
never hurts to sample more. Now we can summarize these samples to find
the mean and 90% credible interval.

In [1]:
θ_mean = mean(post_samples)
θ_ci = quantile(post_samples, [0.05, 0.95])

@show θ_mean * 100;
@show θ_ci;

θ_mean * 100 = 11.594260902070134
θ_ci = [0.03840318830527911, 0.20848848016469992]

So our mean cheating probability given the data is 12% with a 90%
credible interval of (4%, (21%). This suggests a generally low rate of
cheating, though whether the upper limit of the 90% CI is acceptable is
subjective.

One question we should always ask ourselves is the extent to which our
inferences from a Bayesian model are driven be the prior, rather than
the likelihood. Let’s redo our analysis with a less informative (more
permissive) prior to see if we end up with similar inferences. We can
try a Beta(2, 10) distribution, as shown in
<a href="#fig-p1-prior-comparison" class="quarto-xref">Figure 3</a>, but
there are many other choices.

In [1]:
θ = 0:0.01:1
plot(θ, pdf.(Beta(3, 80), θ), lw=2, label="Original Prior", xlabel="θ", ylabel="Density")
plot!(θ, pdf.(Beta(2, 10), θ), lw=2, label="Alternate Prior")

Let’s repeat the entire analysis from before and see what the posterior
mean and 90% credible intervals look like. First we need to find the new
upper bound on the posterior density.

In [1]:
lprior_alt(θ) = logpdf(Beta(2, 10), θ)
lposterior_alt(θ, y) = lprior_alt(θ) + llikelihood(θ, y)

θ = 0:0.005:1
lp = lposterior_alt.(θ, 40)
plot(θ, exp.(lp))

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip080)" d="M220.842 1834 Q217.231 1834 215.403 1837.57 Q213.597 1841.11 213.597 1848.24 Q213.597 1855.34 215.403 1858.91 Q217.231 1862.45 220.842 1862.45 Q224.477 1862.45 226.282 1858.91 Q228.111 1855.34 228.111 1848.24 Q228.111 1841.11 226.282 1837.57 Q224.477 1834 220.842 1834 M220.842 1830.3 Q226.653 1830.3 229.708 1834.9 Q232.787 1839.49 232.787 1848.24 Q232.787 1856.96 229.708 1861.57 Q226.653 1866.15 220.842 1866.15 Q215.032 1866.15 211.954 1861.57 Q208.898 1856.96 208.898 1848.24 Q208.898 1839.49 211.954 1834.9 Q215.032 1830.3 220.842 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip080)" d="M266.074 1834 Q262.463 1834 260.634 1837.57 Q258.828 1841.11 258.828 1848.24 Q258.828 1855.34 260.634 1858.91 Q262.463 1862.45 266.074 1862.45 Q269.708 1862.45 271.513 1858.91 Q273.342 1855.34 273.342 1848.24 Q273.342 1841.11 271.513 1837.57 Q269.708 1834 266.074 1834 M266.074 1830.3 Q271.884 1830.3 274.939 1834.9 Q278.018 1839.49 278.018 1848.24 Q278.018 1856.96 274.939 1861.57 Q271.884 1866.15 266.074 1866.15 Q260.263 1866.15 257.185 1861.57 Q254.129 1856.96 254.129 1848.24 Q254.129 1839.49 257.185 1834.9 Q260.263 1830.3 266.074 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip080)" d="M296.236 1834 Q292.624 1834 290.796 1837.57 Q288.99 1841.11 288.99 1848.24 Q288.99 1855.34 290.796 1858.91 Q292.624 1862.45 296.236 1862.45 Q299.87 1862.45 301.675 1858.91 Q303.504 1855.34 303.504 1848.24 Q303.504 1841.11 301.675 1837.57 Q299.87 1834 296.236 1834 M296.236 1830.3 Q302.046 1830.3 305.101 1834.9 Q308.18 1839.49 308.18 1848.24 Q308.18 1856.96 305.101 1861.57 Q302.046 1866.15 296.236 1866.15 Q290.425 1866.15 287.347 1861.57 Q284.291 1856.96 284.291 1848.24 Q284.291 1839.49 287.347 1834.9 Q290.425 1830.3 296.236 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip080)" d="M799.548 1834 Q795.937 1834 794.108 1837.57 Q792.303 1841.11 792.303 1848.24 Q792.303 1855.34 794.108 1858.91 Q795.937 1862.45 799.548 1862.45 Q803.182 1862.45 804.988 1858.91 Q806.817 1855.34 806.817 1848.24 Q806.817 1841.11 804.988 1837.57 Q803.182 1834 799.548 1834 M799.548 1830.3 Q805.358 1830.3 808.414 1834.9 Q811.492 1839.49 811.492 1848.24 Q811.492 1856.96 808.414 1861.57 Q805.358 1866.15 799.548 1866.15 Q793.738 1866.15 790.659 1861.57 Q787.604 1856.96 787.604 1848.24 Q787.604 1839.49 790.659 1834.9 Q793.738 1830.3 799.548 1830.3 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip080)" d="M838.807 1861.55 L855.126 1861.55 L855.126 1865.48 L833.182 1865.48 L833.182 1861.55 Q835.844 1858.79 840.427 1854.16 Q845.034 1849.51 846.214 1848.17 Q848.46 1845.65 849.339 1843.91 Q850.242 1842.15 850.242 1840.46 Q850.242 1837.71 848.298 1835.97 Q846.377 1834.23 843.275 1834.23 Q841.076 1834.23 838.622 1835 Q836.191 1835.76 833.414 1837.31 L833.414 1832.59 Q836.238 1831.46 838.691 1830.88 Q841.145 1830.3 843.182 1830.3 Q848.552 1830.3 851.747 1832.98 Q854.941 1835.67 854.941 1840.16 Q854.941 1842.29 854.131 1844.21 Q853.344 1846.11 851.238 1848.7 Q850.659 1849.37 847.557 1852.59 Q844.455 1855.78 838.807 1861.55 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip080)" d="M864.988 1830.92 L883.344 1830.92 L883.344 1834.86 L869.27 1834.86 L869.27 1843.33 Q870.288 1842.98 871.307 1842.82 Q872.325 1842.64 873.344 1842.64 Q879.131 1842.64 882.511 1845.81 Q885.89 1848.98 885.89 1854.4 Q885.89 1859.97 882.418 1863.08 Q878.946 1866.15 872.626 1866.15 Q870.45 1866.15 868.182 1865.78 Q865.937 1865.41 863.529 1864.67 L863.529 1859.97 Q865.613 1861.11 867.835 1861.66 Q870.057 1862.22 872.534 1862.22 Q876.538 1862.22 878.876 1860.11 Q881.214 1858.01 881.214 1854.4 Q881.214 1850.78 878.876 1848.68 Q876.538 1846.57 872.534 1846.57 Q870.659 1846.57 868.784 1846.99 Q866.932 1847.4 864

So using $M=0.2$ will work, which we will do to finish the sampling.

In [1]:
post_samples = zeros(1_000)
# we will use a counter to keep count of how many samples we've kept
kept_samples = 0
while kept_samples < 1_000
    # generate a proposal
    x = rand(Uniform(0, 1))
    u = rand(Uniform(0, 1))
    if 0.2 * u < exp(lposterior_alt(x, 40))
        kept_samples += 1
        post_samples[kept_samples] = x
    end
end

θ_mean = mean(post_samples)
θ_ci = quantile(post_samples, [0.05, 0.95])

@show θ_mean * 100;
@show θ_ci;

θ_mean * 100 = 23.7464694628426
θ_ci = [0.1137444002256321, 0.37512811469430585]

We can see that the use of this alternate prior has resulted in a much
higher estimate and larger uncertainties. This suggests that our prior
is doing a lot of work in how we interpret the outcomes of the testing
procedure, and it might result in too much ambiguity to get a sense of
how much of the class is actually cheating, as with our original prior,
we estimated 12% of the class was cheating, while with this broader
prior, we estimate 24% is cheating, with potentially up to around 40%.

### Problem 2

First, we need to fit the extreme water distribution to the provided
data.

In [1]:
# load data
dat = CSV.read("data/water_depths.csv", DataFrame)
# fit LogNormal distribution
wl_dist = fit(LogNormal, dat.depths)

Distributions.LogNormal{Float64}(μ=0.14057503250689243, σ=0.25281750343529374)

We can see how the fitted distribution matches the data.

In [1]:
histogram(dat.depths, xlabel="Annual Max Water Level (m)", ylabel="Density", normalize=:pdf, label="Data")
plot!(wl_dist, color=:red, lw=2, label="Fitted Distribution")

> **Important**
>
> If you used an optimization routine to find the lognormal parameters,
> the scale parameter will differ at the thousandths place. It appears
> this is enough to shift all of the subsequent estimates downward by
> around \$3,000.

Now let’s draw samples. Note that, at some point, we will need to shift
these by 1.5m to capture the flooding depth at the house, so we may as
well do that here.

In [1]:
nsamp = 10_000
wl_samples = rand(wl_dist, nsamp)
wl_samples_shift = wl_samples .- 1.5
histogram(wl_samples, xlabel="Annual Max Water Level (m)", ylabel="Count", label="Stream", alpha=0.5)
histogram!(wl_samples_shift, label="House", alpha=0.5)

Let’s define our depth-damage function,
$$d(h) = \mathbb{I}[h > 0] \frac{1}{1+\exp(-k(x-x_0))},$$ with
$k = 1.25$ and $x_0 = 2$.

In [1]:
h = 0:0.01:5
dd(h, k, x₀) = (h .> 0) * 1 ./ (1 .+ exp.(-k * (h .- x₀)))
plot(h, dd(h, 1.25, 2), lw=2, xlabel="Flood Depth (m Above Base Elevation)", ylabel="Fraction of Value Damaged", legend=false)
ylims!(0, 1)

Finally, to conduct the Monte Carlo simulation we propagate our shifted
water level samples through the depth-damage function. Since the
depth-damage function `dd` gives us the fraction of value that is
damaged, we also need to multiply by the value of the house.

``` julia
dd_samples = 400_000 * dd(wl_samples_shift, 1.25, 2)
p1 = histogram(dd_samples, xlabel="Annual Damaged Value (\$)", ylabel="Count")
p2 = histogram(dd_samples[dd_samples .> 0], xlabel="Annual Damaged Value (\$)", ylabel="Count")
xlims!(p2, (0, 90_000))
display(p1)
display(p2)
```

<table>
<colgroup>
<col style="width: 50%" />
<col style="width: 50%" />
</colgroup>
<tbody>
<tr>
<td style="text-align: left;"><div width="50.0%"
data-layout-align="left">
<div>
<?xml version="1.0" encoding="utf-8"?>
<svg xmlns="http://www.w3.org/2000/svg" xmlns:xlink="http://www.w3.org/1999/xlink" width="672" height="480" viewBox="0 0 2688 1920">
<defs>
  <clipPath id="clip320">
    <rect x="0" y="0" width="2688" height="1920"/>
  </clipPath>
</defs>
<path clip-path="url(#clip320)" d="M0 1920 L2688 1920 L2688 -4.26326e-14 L0 -4.26326e-14  Z" fill="#ffffff" fill-rule="evenodd" fill-opacity="1"/>
<defs>
  <clipPath id="clip321">
    <rect x="537" y="0" width="1883" height="1883"/>
  </clipPath>
</defs>
<path clip-path="url(#clip320)" d="M271.719 1720.96 L2640.76 1720.96 L2640.76 47.2441 L271.719 47.2441  Z" fill="#ffffff" fill-rule="evenodd" fill-opacity="1"/>
<defs>
  <clipPath id="clip322">
    <rect x="271" y="47" width="2370" height="1675"/>
  </clipPath>
</defs>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="402.02,1720.96 402.02,47.2441 "/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="1106.33,1720.96 1106.33,47.2441 "/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="1810.65,1720.96 1810.65,47.2441 "/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="2514.96,1720.96 2514.96,47.2441 "/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="271.719,1720.96 2640.76,1720.96 "/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="271.719,1327.65 2640.76,1327.65 "/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="271.719,934.345 2640.76,934.345 "/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="271.719,541.039 2640.76,541.039 "/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="271.719,147.734 2640.76,147.734 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="271.719,1720.96 2640.76,1720.96 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="402.02,1720.96 402.02,1702.06 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1106.33,1720.96 1106.33,1702.06 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1810.65,1720.96 1810.65,1702.06 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2514.96,1720.96 2514.96,1702.06 "/>
<path clip-path="url(#clip320)" d="M402.02 1754.18 Q398.409 1754.18 396.58 1757.74 Q394.775 1761.29 394.775 1768.42 Q394.775 1775.52 396.58 1779.09 Q398.409 1782.63 402.02 1782.63 Q405.654 1782.63 407.46 1779.09 Q409.289 1775.52 409.289 1768.42 Q409.289 1761.29 407.46 1757.74 Q405.654 1754.18 402.02 1754.18 M402.02 1750.48 Q407.83 1750.48 410.886 1755.08 Q413.965 1759.67 413.965 1768.42 Q413.965 1777.14 410.886 1781.75 Q407.83 1786.33 402.02 1786.33 Q396.21 1786.33 393.131 1781.75 Q390.076 1777.14 390.076 1768.42 Q390.076 1759.67 393.131 1755.08 Q396.21 1750.48 402.02 1750.48 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M998.164 1766.76 L1016.52 1766.76 L1016.52 1770.7 L1002.45 1770.7 L1002.45 1779.17 Q1003.46 1778.82 1004.48 1778.66 Q1005.5 1778.47 1006.52 1778.47 Q1012.31 1778.47 1015.69 1781.64 Q1019.07 1784.82 1019.07 1790.23 Q1019.07 1795.81 1015.59 1798.91 Q1012.12 1801.99 1005.8 1801.99 Q1003.63 1801.99 1001.36 1801.62 Q999.113 1801.25 996.705 1800.51 L996.705 1795.81 Q998.789 1796.95 1001.01 1797.5 Q1003.23 1798.06 1005.71 1798.06 Q1009.71 1798.06 1012.05 1795.95 Q1014.39 1793.84 1014.39 1790.23 Q1014.39 1786.62 1012.05 1784.51 Q1009.71 1782.41 1005.71 1782.41 Q1003.83 1782.41 1001.96 1782.83 Q1000.11 1783.24 998.164 1784.12 L998.164 1766.76 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1028.28 1795.44 L1033.16 1795.44 L1033.16 1801.32 L1028.28 1801.32 L1028.28 1795.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1053.35 1769.84 Q1049.74 1769.84 1047.91 1773.4 Q1046.1 1776.95 1046.1 1784.08 Q1046.1 1791.18 1047.91 1794.75 Q1049.74 1798.29 1053.35 1798.29 Q1056.98 1798.29 1058.79 1794.75 Q1060.62 1791.18 1060.62 1784.08 Q1060.62 1776.95 1058.79 1773.4 Q1056.98 1769.84 1053.35 1769.84 M1053.35 1766.14 Q1059.16 1766.14 1062.21 1770.74 Q1065.29 1775.33 1065.29 1784.08 Q1065.29 1792.8 1062.21 1797.41 Q1059.16 1801.99 1053.35 1801.99 Q1047.54 1801.99 1044.46 1797.41 Q1041.4 1792.8 1041.4 1784.08 Q1041.4 1775.33 1044.46 1770.74 Q1047.54 1766.14 1053.35 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1083.51 1769.84 Q1079.9 1769.84 1078.07 1773.4 Q1076.26 1776.95 1076.26 1784.08 Q1076.26 1791.18 1078.07 1794.75 Q1079.9 1798.29 1083.51 1798.29 Q1087.14 1798.29 1088.95 1794.75 Q1090.78 1791.18 1090.78 1784.08 Q1090.78 1776.95 1088.95 1773.4 Q1087.14 1769.84 1083.51 1769.84 M1083.51 1766.14 Q1089.32 1766.14 1092.38 1770.74 Q1095.45 1775.33 1095.45 1784.08 Q1095.45 1792.8 1092.38 1797.41 Q1089.32 1801.99 1083.51 1801.99 Q1077.7 1801.99 1074.62 1797.41 Q1071.57 1792.8 1071.57 1784.08 Q1071.57 1775.33 1074.62 1770.74 Q1077.7 1766.14 1083.51 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1131.84 1775.86 L1121.26 1786.48 L1131.84 1797.06 L1129.09 1799.86 L1118.46 1789.24 L1107.84 1799.86 L1105.11 1797.06 L1115.66 1786.48 L1105.11 1775.86 L1107.84 1773.06 L1118.46 1783.68 L1129.09 1773.06 L1131.84 1775.86 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1144.2 1797.39 L1151.84 1797.39 L1151.84 1771.02 L1143.53 1772.69 L1143.53 1768.43 L1151.8 1766.76 L1156.47 1766.76 L1156.47 1797.39 L1164.11 1797.39 L1164.11 1801.32 L1144.2 1801.32 L1144.2 1797.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1183.56 1769.84 Q1179.94 1769.84 1178.12 1773.4 Q1176.31 1776.95 1176.31 1784.08 Q1176.31 1791.18 1178.12 1794.75 Q1179.94 1798.29 1183.56 1798.29 Q1187.19 1798.29 1189 1794.75 Q1190.82 1791.18 1190.82 1784.08 Q1190.82 1776.95 1189 1773.4 Q1187.19 1769.84 1183.56 1769.84 M1183.56 1766.14 Q1189.37 1766.14 1192.42 1770.74 Q1195.5 1775.33 1195.5 1784.08 Q1195.5 1792.8 1192.42 1797.41 Q1189.37 1801.99 1183.56 1801.99 Q1177.75 1801.99 1174.67 1797.41 Q1171.61 1792.8 1171.61 1784.08 Q1171.61 1775.33 1174.67 1770.74 Q1177.75 1766.14 1183.56 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1208.18 1749.14 L1198.58 1764.13 L1208.18 1764.13 L1208.18 1749.14 M1207.18 1745.83 L1211.96 1745.83 L1211.96 1764.13 L1215.96 1764.13 L1215.96 1767.29 L1211.96 1767.29 L1211.96 1773.91 L1208.18 1773.91 L1208.18 1767.29 L1195.5 1767.29 L1195.5 1763.62 L1207.18 1745.83 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1703.61 1797.39 L1711.25 1797.39 L1711.25 1771.02 L1702.94 1772.69 L1702.94 1768.43 L1711.21 1766.76 L1715.88 1766.76 L1715.88 1797.39 L1723.52 1797.39 L1723.52 1801.32 L1703.61 1801.32 L1703.61 1797.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1732.96 1795.44 L1737.85 1795.44 L1737.85 1801.32 L1732.96 1801.32 L1732.96 1795.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1758.03 1769.84 Q1754.42 1769.84 1752.59 1773.4 Q1750.79 1776.95 1750.79 1784.08 Q1750.79 1791.18 1752.59 1794.75 Q1754.42 1798.29 1758.03 1798.29 Q1761.67 1798.29 1763.47 1794.75 Q1765.3 1791.18 1765.3 1784.08 Q1765.3 1776.95 1763.47 1773.4 Q1761.67 1769.84 1758.03 1769.84 M1758.03 1766.14 Q1763.84 1766.14 1766.9 1770.74 Q1769.98 1775.33 1769.98 1784.08 Q1769.98 1792.8 1766.9 1797.41 Q1763.84 1801.99 1758.03 1801.99 Q1752.22 1801.99 1749.15 1797.41 Q1746.09 1792.8 1746.09 1784.08 Q1746.09 1775.33 1749.15 1770.74 Q1752.22 1766.14 1758.03 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1788.2 1769.84 Q1784.59 1769.84 1782.76 1773.4 Q1780.95 1776.95 1780.95 1784.08 Q1780.95 1791.18 1782.76 1794.75 Q1784.59 1798.29 1788.2 1798.29 Q1791.83 1798.29 1793.64 1794.75 Q1795.46 1791.18 1795.46 1784.08 Q1795.46 1776.95 1793.64 1773.4 Q1791.83 1769.84 1788.2 1769.84 M1788.2 1766.14 Q1794.01 1766.14 1797.06 1770.74 Q1800.14 1775.33 1800.14 1784.08 Q1800.14 1792.8 1797.06 1797.41 Q1794.01 1801.99 1788.2 1801.99 Q1782.39 1801.99 1779.31 1797.41 Q1776.25 1792.8 1776.25 1784.08 Q1776.25 1775.33 1779.31 1770.74 Q1782.39 1766.14 1788.2 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1836.53 1775.86 L1825.95 1786.48 L1836.53 1797.06 L1833.77 1799.86 L1823.15 1789.24 L1812.52 1799.86 L1809.79 1797.06 L1820.35 1786.48 L1809.79 1775.86 L1812.52 1773.06 L1823.15 1783.68 L1833.77 1773.06 L1836.53 1775.86 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1848.89 1797.39 L1856.53 1797.39 L1856.53 1771.02 L1848.22 1772.69 L1848.22 1768.43 L1856.48 1766.76 L1861.16 1766.76 L1861.16 1797.39 L1868.8 1797.39 L1868.8 1801.32 L1848.89 1801.32 L1848.89 1797.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1888.24 1769.84 Q1884.63 1769.84 1882.8 1773.4 Q1881 1776.95 1881 1784.08 Q1881 1791.18 1882.8 1794.75 Q1884.63 1798.29 1888.24 1798.29 Q1891.88 1798.29 1893.68 1794.75 Q1895.51 1791.18 1895.51 1784.08 Q1895.51 1776.95 1893.68 1773.4 Q1891.88 1769.84 1888.24 1769.84 M1888.24 1766.14 Q1894.05 1766.14 1897.11 1770.74 Q1900.19 1775.33 1900.19 1784.08 Q1900.19 1792.8 1897.11 1797.41 Q1894.05 1801.99 1888.24 1801.99 Q1882.43 1801.99 1879.35 1797.41 Q1876.3 1792.8 1876.3 1784.08 Q1876.3 1775.33 1879.35 1770.74 Q1882.43 1766.14 1888.24 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1901.37 1745.83 L1916.29 1745.83 L1916.29 1749.03 L1904.85 1749.03 L1904.85 1755.91 Q1905.68 1755.63 1906.51 1755.5 Q1907.33 1755.35 1908.16 1755.35 Q1912.86 1755.35 1915.61 1757.92 Q1918.35 1760.5 1918.35 1764.9 Q1918.35 1769.43 1915.53 1771.95 Q1912.71 1774.46 1907.58 1774.46 Q1905.81 1774.46 1903.97 1774.15 Q1902.14 1773.85 1900.19 1773.25 L1900.19 1769.43 Q1901.88 1770.36 1903.68 1770.81 Q1905.49 1771.26 1907.5 1771.26 Q1910.76 1771.26 1912.66 1769.55 Q1914.56 1767.84 1914.56 1764.9 Q1914.56 1761.97 1912.66 1760.26 Q1910.76 1758.54 1907.5 1758.54 Q1905.98 1758.54 1904.46 1758.88 Q1902.95 1759.22 1901.37 1759.94 L1901.37 1745.83 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2407.93 1797.39 L2415.57 1797.39 L2415.57 1771.02 L2407.26 1772.69 L2407.26 1768.43 L2415.52 1766.76 L2420.2 1766.76 L2420.2 1797.39 L2427.83 1797.39 L2427.83 1801.32 L2407.93 1801.32 L2407.93 1797.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2437.28 1795.44 L2442.16 1795.44 L2442.16 1801.32 L2437.28 1801.32 L2437.28 1795.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2452.39 1766.76 L2470.75 1766.76 L2470.75 1770.7 L2456.68 1770.7 L2456.68 1779.17 Q2457.7 1778.82 2458.71 1778.66 Q2459.73 1778.47 2460.75 1778.47 Q2466.54 1778.47 2469.92 1781.64 Q2473.3 1784.82 2473.3 1790.23 Q2473.3 1795.81 2469.83 1798.91 Q2466.35 1801.99 2460.03 1801.99 Q2457.86 1801.99 2455.59 1801.62 Q2453.34 1801.25 2450.94 1800.51 L2450.94 1795.81 Q2453.02 1796.95 2455.24 1797.5 Q2457.46 1798.06 2459.94 1798.06 Q2463.95 1798.06 2466.28 1795.95 Q2468.62 1793.84 2468.62 1790.23 Q2468.62 1786.62 2466.28 1784.51 Q2463.95 1782.41 2459.94 1782.41 Q2458.07 1782.41 2456.19 1782.83 Q2454.34 1783.24 2452.39 1784.12 L2452.39 1766.76 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2492.51 1769.84 Q2488.9 1769.84 2487.07 1773.4 Q2485.26 1776.95 2485.26 1784.08 Q2485.26 1791.18 2487.07 1794.75 Q2488.9 1798.29 2492.51 1798.29 Q2496.14 1798.29 2497.95 1794.75 Q2499.78 1791.18 2499.78 1784.08 Q2499.78 1776.95 2497.95 1773.4 Q2496.14 1769.84 2492.51 1769.84 M2492.51 1766.14 Q2498.32 1766.14 2501.38 1770.74 Q2504.45 1775.33 2504.45 1784.08 Q2504.45 1792.8 2501.38 1797.41 Q2498.32 1801.99 2492.51 1801.99 Q2486.7 1801.99 2483.62 1797.41 Q2480.57 1792.8 2480.57 1784.08 Q2480.57 1775.33 2483.62 1770.74 Q2486.7 1766.14 2492.51 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2540.84 1775.86 L2530.26 1786.48 L2540.84 1797.06 L2538.09 1799.86 L2527.46 1789.24 L2516.84 1799.86 L2514.11 1797.06 L2524.66 1786.48 L2514.11 1775.86 L2516.84 1773.06 L2527.46 1783.68 L2538.09 1773.06 L2540.84 1775.86 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2553.2 1797.39 L2560.84 1797.39 L2560.84 1771.02 L2552.53 1772.69 L2552.53 1768.43 L2560.8 1766.76 L2565.47 1766.76 L2565.47 1797.39 L2573.11 1797.39 L2573.11 1801.32 L2553.2 1801.32 L2553.2 1797.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2592.56 1769.84 Q2588.94 1769.84 2587.12 1773.4 Q2585.31 1776.95 2585.31 1784.08 Q2585.31 1791.18 2587.12 1794.75 Q2588.94 1798.29 2592.56 1798.29 Q2596.19 1798.29 2598 1794.75 Q2599.82 1791.18 2599.82 1784.08 Q2599.82 1776.95 2598 1773.4 Q2596.19 1769.84 2592.56 1769.84 M2592.56 1766.14 Q2598.37 1766.14 2601.42 1770.74 Q2604.5 1775.33 2604.5 1784.08 Q2604.5 1792.8 2601.42 1797.41 Q2598.37 1801.99 2592.56 1801.99 Q2586.75 1801.99 2583.67 1797.41 Q2580.61 1792.8 2580.61 1784.08 Q2580.61 1775.33 2583.67 1770.74 Q2586.75 1766.14 2592.56 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2605.69 1745.83 L2620.6 1745.83 L2620.6 1749.03 L2609.16 1749.03 L2609.16 1755.91 Q2609.99 1755.63 2610.82 1755.5 Q2611.65 1755.35 2612.47 1755.35 Q2617.18 1755.35 2619.92 1757.92 Q2622.67 1760.5 2622.67 1764.9 Q2622.67 1769.43 2619.85 1771.95 Q2617.03 1774.46 2611.89 1774.46 Q2610.12 1774.46 2608.28 1774.15 Q2606.46 1773.85 2604.5 1773.25 L2604.5 1769.43 Q2606.19 1770.36 2608 1770.81 Q2609.8 1771.26 2611.82 1771.26 Q2615.07 1771.26 2616.97 1769.55 Q2618.87 1767.84 2618.87 1764.9 Q2618.87 1761.97 2616.97 1760.26 Q2615.07 1758.54 2611.82 1758.54 Q2610.29 1758.54 2608.77 1758.88 Q2607.27 1759.22 2605.69 1759.94 L2605.69 1745.83 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1042.8 1847.38 L1034.08 1871.03 L1051.55 1871.03 L1042.8 1847.38 M1039.17 1841.05 L1046.46 1841.05 L1064.57 1888.57 L1057.89 1888.57 L1053.56 1876.37 L1032.14 1876.37 L1027.81 1888.57 L1021.03 1888.57 L1039.17 1841.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1100.89 1867.05 L1100.89 1888.57 L1095.03 1888.57 L1095.03 1867.24 Q1095.03 1862.18 1093.06 1859.66 Q1091.08 1857.15 1087.14 1857.15 Q1082.4 1857.15 1079.66 1860.17 Q1076.92 1863.2 1076.92 1868.42 L1076.92 1888.57 L1071.03 1888.57 L1071.03 1852.92 L1076.92 1852.92 L1076.92 1858.46 Q1079.02 1855.24 1081.85 1853.65 Q1084.72 1852.06 1088.44 1852.06 Q1094.59 1852.06 1097.74 1855.88 Q1100.89 1859.66 1100.89 1867.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1142.2 1867.05 L1142.2 1888.57 L1136.34 1888.57 L1136.34 1867.24 Q1136.34 1862.18 1134.37 1859.66 Q1132.4 1857.15 1128.45 1857.15 Q1123.71 1857.15 1120.97 1860.17 Q1118.23 1863.2 1118.23 1868.42 L1118.23 1888.57 L1112.35 1888.57 L1112.35 1852.92 L1118.23 1852.92 L1118.23 1858.46 Q1120.34 1855.24 1123.17 1853.65 Q1126.03 1852.06 1129.76 1852.06 Q1135.9 1852.06 1139.05 1855.88 Q1142.2 1859.66 1142.2 1867.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1153.28 1874.5 L1153.28 1852.92 L1159.13 1852.92 L1159.13 1874.27 Q1159.13 1879.33 1161.11 1881.88 Q1163.08 1884.4 1167.03 1884.4 Q1171.77 1884.4 1174.51 1881.37 Q1177.28 1878.35 1177.28 1873.13 L1177.28 1852.92 L1183.13 1852.92 L1183.13 1888.57 L1177.28 1888.57 L1177.28 1883.09 Q1175.14 1886.34 1172.31 1887.93 Q1169.51 1889.49 1165.79 1889.49 Q1159.64 1889.49 1156.46 1885.67 Q1153.28 1881.85 1153.28 1874.5 M1168.01 1852.06 L1168.01 1852.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1211.4 1870.65 Q1204.3 1870.65 1201.56 1872.27 Q1198.82 1873.89 1198.82 1877.81 Q1198.82 1880.93 1200.86 1882.77 Q1202.93 1884.59 1206.46 1884.59 Q1211.33 1884.59 1214.26 1881.15 Q1217.22 1877.68 1217.22 1871.95 L1217.22 1870.65 L1211.4 1870.65 M1223.08 1868.23 L1223.08 1888.57 L1217.22 1888.57 L1217.22 1883.15 Q1215.22 1886.4 1212.22 1887.96 Q1209.23 1889.49 1204.9 1889.49 Q1199.43 1889.49 1196.18 1886.43 Q1192.97 1883.35 1192.97 1878.19 Q1192.97 1872.17 1196.98 1869.12 Q1201.02 1866.06 1209.01 1866.06 L1217.22 1866.06 L1217.22 1865.49 Q1217.22 1861.45 1214.55 1859.25 Q1211.91 1857.02 1207.1 1857.02 Q1204.04 1857.02 1201.15 1857.76 Q1198.25 1858.49 1195.58 1859.95 L1195.58 1854.54 Q1198.79 1853.3 1201.82 1852.69 Q1204.84 1852.06 1207.7 1852.06 Q1215.44 1852.06 1219.26 1856.07 Q1223.08 1860.08 1223.08 1868.23 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1235.14 1839.04 L1241 1839.04 L1241 1888.57 L1235.14 1888.57 L1235.14 1839.04 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1280.66 1846.33 L1280.66 1883.28 L1288.42 1883.28 Q1298.26 1883.28 1302.81 1878.83 Q1307.39 1874.37 1307.39 1864.76 Q1307.39 1855.21 1302.81 1850.78 Q1298.26 1846.33 1288.42 1846.33 L1280.66 1846.33 M1274.23 1841.05 L1287.43 1841.05 Q1301.25 1841.05 1307.71 1846.81 Q1314.17 1852.54 1314.17 1864.76 Q1314.17 1877.04 1307.68 1882.8 Q1301.18 1888.57 1287.43 1888.57 L1274.23 1888.57 L1274.23 1841.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1340.37 1870.65 Q1333.27 1870.65 1330.53 1872.27 Q1327.79 1873.89 1327.79 1877.81 Q1327.79 1880.93 1329.83 1882.77 Q1331.9 1884.59 1335.43 1884.59 Q1340.3 1884.59 1343.23 1881.15 Q1346.19 1877.68 1346.19 1871.95 L1346.19 1870.65 L1340.37 1870.65 M1352.05 1868.23 L1352.05 1888.57 L1346.19 1888.57 L1346.19 1883.15 Q1344.19 1886.4 1341.19 1887.96 Q1338.2 1889.49 1333.87 1889.49 Q1328.4 1889.49 1325.15 1886.43 Q1321.94 1883.35 1321.94 1878.19 Q1321.94 1872.17 1325.95 1869.12 Q1329.99 1866.06 1337.98 1866.06 L1346.19 1866.06 L1346.19 1865.49 Q1346.19 1861.45 1343.52 1859.25 Q1340.87 1857.02 1336.07 1857.02 Q1333.01 1857.02 1330.12 1857.76 Q1327.22 1858.49 1324.55 1859.95 L1324.55 1854.54 Q1327.76 1853.3 1330.79 1852.69 Q1333.81 1852.06 1336.67 1852.06 Q1344.41 1852.06 1348.23 1856.07 Q1352.05 1860.08 1352.05 1868.23 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1391.86 1859.76 Q1394.06 1855.81 1397.12 1853.94 Q1400.17 1852.06 1404.31 1852.06 Q1409.88 1852.06 1412.9 1855.97 Q1415.93 1859.86 1415.93 1867.05 L1415.93 1888.57 L1410.04 1888.57 L1410.04 1867.24 Q1410.04 1862.12 1408.22 1859.63 Q1406.41 1857.15 1402.69 1857.15 Q1398.13 1857.15 1395.49 1860.17 Q1392.85 1863.2 1392.85 1868.42 L1392.85 1888.57 L1386.96 1888.57 L1386.96 1867.24 Q1386.96 1862.08 1385.15 1859.63 Q1383.33 1857.15 1379.55 1857.15 Q1375.06 1857.15 1372.42 1860.21 Q1369.78 1863.23 1369.78 1868.42 L1369.78 1888.57 L1363.89 1888.57 L1363.89 1852.92 L1369.78 1852.92 L1369.78 1858.46 Q1371.78 1855.18 1374.58 1853.62 Q1377.38 1852.06 1381.23 1852.06 Q1385.12 1852.06 1387.82 1854.03 Q1390.56 1856 1391.86 1859.76 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1443.81 1870.65 Q1436.71 1870.65 1433.97 1872.27 Q1431.24 1873.89 1431.24 1877.81 Q1431.24 1880.93 1433.27 1882.77 Q1435.34 1884.59 1438.87 1884.59 Q1443.74 1884.59 1446.67 1881.15 Q1449.63 1877.68 1449.63 1871.95 L1449.63 1870.65 L1443.81 1870.65 M1455.49 1868.23 L1455.49 1888.57 L1449.63 1888.57 L1449.63 1883.15 Q1447.63 1886.4 1444.64 1887.96 Q1441.64 1889.49 1437.32 1889.49 Q1431.84 1889.49 1428.59 1886.43 Q1425.38 1883.35 1425.38 1878.19 Q1425.38 1872.17 1429.39 1869.12 Q1433.43 1866.06 1441.42 1866.06 L1449.63 1866.06 L1449.63 1865.49 Q1449.63 1861.45 1446.96 1859.25 Q1444.32 1857.02 1439.51 1857.02 Q1436.46 1857.02 1433.56 1857.76 Q1430.66 1858.49 1427.99 1859.95 L1427.99 1854.54 Q1431.2 1853.3 1434.23 1852.69 Q1437.25 1852.06 1440.12 1852.06 Q1447.85 1852.06 1451.67 1856.07 Q1455.49 1860.08 1455.49 1868.23 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1491.01 1870.33 Q1491.01 1863.96 1488.37 1860.46 Q1485.76 1856.96 1481.02 1856.96 Q1476.31 1856.96 1473.66 1860.46 Q1471.05 1863.96 1471.05 1870.33 Q1471.05 1876.66 1473.66 1880.16 Q1476.31 1883.66 1481.02 1883.66 Q1485.76 1883.66 1488.37 1880.16 Q1491.01 1876.66 1491.01 1870.33 M1496.87 1884.14 Q1496.87 1893.24 1492.82 1897.67 Q1488.78 1902.12 1480.44 1902.12 Q1477.36 1902.12 1474.62 1901.65 Q1471.88 1901.2 1469.3 1900.25 L1469.3 1894.55 Q1471.88 1895.95 1474.4 1896.62 Q1476.91 1897.29 1479.52 1897.29 Q1485.28 1897.29 1488.15 1894.26 Q1491.01 1891.27 1491.01 1885.19 L1491.01 1882.29 Q1489.2 1885.45 1486.36 1887.01 Q1483.53 1888.57 1479.58 1888.57 Q1473.03 1888.57 1469.02 1883.57 Q1465.01 1878.57 1465.01 1870.33 Q1465.01 1862.05 1469.02 1857.05 Q1473.03 1852.06 1479.58 1852.06 Q1483.53 1852.06 1486.36 1853.62 Q1489.2 1855.18 1491.01 1858.33 L1491.01 1852.92 L1496.87 1852.92 L1496.87 1884.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1539.42 1869.28 L1539.42 1872.14 L1512.49 1872.14 Q1512.88 1878.19 1516.12 1881.37 Q1519.4 1884.52 1525.23 1884.52 Q1528.6 1884.52 1531.75 1883.7 Q1534.93 1882.87 1538.05 1881.21 L1538.05 1886.75 Q1534.9 1888.09 1531.59 1888.79 Q1528.28 1889.49 1524.88 1889.49 Q1516.35 1889.49 1511.35 1884.52 Q1506.38 1879.56 1506.38 1871.09 Q1506.38 1862.34 1511.09 1857.21 Q1515.84 1852.06 1523.86 1852.06 Q1531.05 1852.06 1535.22 1856.7 Q1539.42 1861.32 1539.42 1869.28 M1533.56 1867.56 Q1533.5 1862.75 1530.86 1859.89 Q1528.25 1857.02 1523.92 1857.02 Q1519.02 1857.02 1516.06 1859.79 Q1513.13 1862.56 1512.69 1867.59 L1533.56 1867.56 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1572.49 1858.33 L1572.49 1839.04 L1578.35 1839.04 L1578.35 1888.57 L1572.49 1888.57 L1572.49 1883.22 Q1570.65 1886.4 1567.81 1887.96 Q1565.01 1889.49 1561.06 1889.49 Q1554.6 1889.49 1550.53 1884.33 Q1546.49 1879.18 1546.49 1870.77 Q1546.49 1862.37 1550.53 1857.21 Q1554.6 1852.06 1561.06 1852.06 Q1565.01 1852.06 1567.81 1853.62 Q1570.65 1855.15 1572.49 1858.33 M1552.53 1870.77 Q1552.53 1877.23 1555.18 1880.93 Q1557.85 1884.59 1562.5 1884.59 Q1567.14 1884.59 1569.82 1880.93 Q1572.49 1877.23 1572.49 1870.77 Q1572.49 1864.31 1569.82 1860.65 Q1567.14 1856.96 1562.5 1856.96 Q1557.85 1856.96 1555.18 1860.65 Q1552.53 1864.31 1552.53 1870.77 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1623.64 1888.57 L1605.5 1841.05 L1612.21 1841.05 L1627.27 1881.05 L1642.35 1841.05 L1649.04 1841.05 L1630.93 1888.57 L1623.64 1888.57 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1666.86 1870.65 Q1659.77 1870.65 1657.03 1872.27 Q1654.29 1873.89 1654.29 1877.81 Q1654.29 1880.93 1656.33 1882.77 Q1658.4 1884.59 1661.93 1884.59 Q1666.8 1884.59 1669.73 1881.15 Q1672.69 1877.68 1672.69 1871.95 L1672.69 1870.65 L1666.86 1870.65 M1678.54 1868.23 L1678.54 1888.57 L1672.69 1888.57 L1672.69 1883.15 Q1670.68 1886.4 1667.69 1887.96 Q1664.7 1889.49 1660.37 1889.49 Q1654.9 1889.49 1651.65 1886.43 Q1648.43 1883.35 1648.43 1878.19 Q1648.43 1872.17 1652.44 1869.12 Q1656.49 1866.06 1664.48 1866.06 L1672.69 1866.06 L1672.69 1865.49 Q1672.69 1861.45 1670.01 1859.25 Q1667.37 1857.02 1662.57 1857.02 Q1659.51 1857.02 1656.61 1857.76 Q1653.72 1858.49 1651.04 1859.95 L1651.04 1854.54 Q1654.26 1853.3 1657.28 1852.69 Q1660.31 1852.06 1663.17 1852.06 Q1670.91 1852.06 1674.72 1856.07 Q1678.54 1860.08 1678.54 1868.23 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1690.61 1839.04 L1696.46 1839.04 L1696.46 1888.57 L1690.61 1888.57 L1690.61 1839.04 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1708.11 1874.5 L1708.11 1852.92 L1713.97 1852.92 L1713.97 1874.27 Q1713.97 1879.33 1715.94 1881.88 Q1717.92 1884.4 1721.86 1884.4 Q1726.6 1884.4 1729.34 1881.37 Q1732.11 1878.35 1732.11 1873.13 L1732.11 1852.92 L1737.97 1852.92 L1737.97 1888.57 L1732.11 1888.57 L1732.11 1883.09 Q1729.98 1886.34 1727.15 1887.93 Q1724.35 1889.49 1720.62 1889.49 Q1714.48 1889.49 1711.3 1885.67 Q1708.11 1881.85 1708.11 1874.5 M1722.85 1852.06 L1722.85 1852.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1780.52 1869.28 L1780.52 1872.14 L1753.6 1872.14 Q1753.98 1878.19 1757.22 1881.37 Q1760.5 1884.52 1766.33 1884.52 Q1769.7 1884.52 1772.85 1883.7 Q1776.03 1882.87 1779.15 1881.21 L1779.15 1886.75 Q1776 1888.09 1772.69 1888.79 Q1769.38 1889.49 1765.98 1889.49 Q1757.45 1889.49 1752.45 1884.52 Q1747.48 1879.56 1747.48 1871.09 Q1747.48 1862.34 1752.2 1857.21 Q1756.94 1852.06 1764.96 1852.06 Q1772.15 1852.06 1776.32 1856.7 Q1780.52 1861.32 1780.52 1869.28 M1774.67 1867.56 Q1774.6 1862.75 1771.96 1859.89 Q1769.35 1857.02 1765.02 1857.02 Q1760.12 1857.02 1757.16 1859.79 Q1754.23 1862.56 1753.79 1867.59 L1774.67 1867.56 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1824.92 1839.1 Q1820.66 1846.42 1818.59 1853.59 Q1816.52 1860.75 1816.52 1868.1 Q1816.52 1875.45 1818.59 1882.68 Q1820.69 1889.87 1824.92 1897.16 L1819.83 1897.16 Q1815.06 1889.68 1812.67 1882.45 Q1810.31 1875.23 1810.31 1868.1 Q1810.31 1861 1812.67 1853.81 Q1815.02 1846.62 1819.83 1839.1 L1824.92 1839.1 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1852.17 1898.15 L1848.99 1898.15 L1848.95 1888.57 Q1845.61 1888.5 1842.27 1887.8 Q1838.93 1887.07 1835.55 1885.64 L1835.55 1879.91 Q1838.8 1881.94 1842.11 1883 Q1845.45 1884.01 1848.99 1884.05 L1848.99 1869.53 Q1841.95 1868.39 1838.74 1865.65 Q1835.55 1862.91 1835.55 1858.14 Q1835.55 1852.95 1839.02 1849.96 Q1842.49 1846.97 1848.99 1846.52 L1848.99 1839.04 L1852.17 1839.04 L1852.17 1846.42 Q1855.13 1846.55 1857.9 1847.06 Q1860.67 1847.54 1863.31 1848.4 L1863.31 1853.97 Q1860.67 1852.63 1857.87 1851.9 Q1855.1 1851.17 1852.17 1851.04 L1852.17 1864.63 Q1859.39 1865.74 1862.8 1868.61 Q1866.2 1871.47 1866.2 1876.44 Q1866.2 1881.82 1862.58 1884.94 Q1858.98 1888.02 1852.17 1888.5 L1852.17 1898.15 M1848.99 1864.06 L1848.99 1851.01 Q1845.29 1851.42 1843.35 1853.11 Q1841.41 1854.8 1841.41 1857.6 Q1841.41 1860.33 1843.19 1861.86 Q1845.01 1863.39 1848.99 1864.06 M1852.17 1870.17 L1852.17 1883.95 Q1856.21 1883.41 1858.25 1881.66 Q1860.32 1879.91 1860.32 1877.04 Q1860.32 1874.24 1858.34 1872.59 Q1856.4 1870.93 1852.17 1870.17 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M1876.84 1839.1 L1881.93 1839.1 Q1886.7 1846.62 1889.06 1853.81 Q1891.44 1861 1891.44 1868.1 Q1891.44 1875.23 1889.06 1882.45 Q1886.7 1889.68 1881.93 1897.16 L1876.84 1897.16 Q1881.07 1889.87 1883.14 1882.68 Q1885.24 1875.45 1885.24 1868.1 Q1885.24 1860.75 1883.14 1853.59 Q1881.07 1846.42 1876.84 1839.1 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="271.719,1720.96 271.719,47.2441 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="271.719,1720.96 290.617,1720.96 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="271.719,1327.65 290.617,1327.65 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="271.719,934.345 290.617,934.345 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="271.719,541.039 290.617,541.039 "/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="271.719,147.734 290.617,147.734 "/>
<path clip-path="url(#clip320)" d="M219.455 1706.76 Q215.844 1706.76 214.015 1710.32 Q212.209 1713.86 212.209 1720.99 Q212.209 1728.1 214.015 1731.66 Q215.844 1735.2 219.455 1735.2 Q223.089 1735.2 224.894 1731.66 Q226.723 1728.1 226.723 1720.99 Q226.723 1713.86 224.894 1710.32 Q223.089 1706.76 219.455 1706.76 M219.455 1703.05 Q225.265 1703.05 228.32 1707.66 Q231.399 1712.24 231.399 1720.99 Q231.399 1729.72 228.32 1734.32 Q225.265 1738.91 219.455 1738.91 Q213.644 1738.91 210.566 1734.32 Q207.51 1729.72 207.51 1720.99 Q207.51 1712.24 210.566 1707.66 Q213.644 1703.05 219.455 1703.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M122.997 1341 L139.316 1341 L139.316 1344.93 L117.372 1344.93 L117.372 1341 Q120.034 1338.24 124.617 1333.61 Q129.224 1328.96 130.404 1327.62 Q132.65 1325.09 133.529 1323.36 Q134.432 1321.6 134.432 1319.91 Q134.432 1317.15 132.488 1315.42 Q130.566 1313.68 127.464 1313.68 Q125.265 1313.68 122.812 1314.44 Q120.381 1315.21 117.603 1316.76 L117.603 1312.04 Q120.427 1310.9 122.881 1310.32 Q125.335 1309.75 127.372 1309.75 Q132.742 1309.75 135.937 1312.43 Q139.131 1315.12 139.131 1319.61 Q139.131 1321.74 138.321 1323.66 Q137.534 1325.56 135.427 1328.15 Q134.849 1328.82 131.747 1332.04 Q128.645 1335.23 122.997 1341 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M159.131 1313.45 Q155.52 1313.45 153.691 1317.01 Q151.886 1320.56 151.886 1327.69 Q151.886 1334.79 153.691 1338.36 Q155.52 1341.9 159.131 1341.9 Q162.765 1341.9 164.571 1338.36 Q166.399 1334.79 166.399 1327.69 Q166.399 1320.56 164.571 1317.01 Q162.765 1313.45 159.131 1313.45 M159.131 1309.75 Q164.941 1309.75 167.997 1314.35 Q171.075 1318.94 171.075 1327.69 Q171.075 1336.41 167.997 1341.02 Q164.941 1345.6 159.131 1345.6 Q153.321 1345.6 150.242 1341.02 Q147.186 1336.41 147.186 1327.69 Q147.186 1318.94 150.242 1314.35 Q153.321 1309.75 159.131 1309.75 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M189.293 1313.45 Q185.682 1313.45 183.853 1317.01 Q182.047 1320.56 182.047 1327.69 Q182.047 1334.79 183.853 1338.36 Q185.682 1341.9 189.293 1341.9 Q192.927 1341.9 194.733 1338.36 Q196.561 1334.79 196.561 1327.69 Q196.561 1320.56 194.733 1317.01 Q192.927 1313.45 189.293 1313.45 M189.293 1309.75 Q195.103 1309.75 198.158 1314.35 Q201.237 1318.94 201.237 1327.69 Q201.237 1336.41 198.158 1341.02 Q195.103 1345.6 189.293 1345.6 Q183.483 1345.6 180.404 1341.02 Q177.348 1336.41 177.348 1327.69 Q177.348 1318.94 180.404 1314.35 Q183.483 1309.75 189.293 1309.75 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M219.455 1313.45 Q215.844 1313.45 214.015 1317.01 Q212.209 1320.56 212.209 1327.69 Q212.209 1334.79 214.015 1338.36 Q215.844 1341.9 219.455 1341.9 Q223.089 1341.9 224.894 1338.36 Q226.723 1334.79 226.723 1327.69 Q226.723 1320.56 224.894 1317.01 Q223.089 1313.45 219.455 1313.45 M219.455 1309.75 Q225.265 1309.75 228.32 1314.35 Q231.399 1318.94 231.399 1327.69 Q231.399 1336.41 228.32 1341.02 Q225.265 1345.6 219.455 1345.6 Q213.644 1345.6 210.566 1341.02 Q207.51 1336.41 207.51 1327.69 Q207.51 1318.94 210.566 1314.35 Q213.644 1309.75 219.455 1309.75 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M131.816 921.139 L120.011 939.588 L131.816 939.588 L131.816 921.139 M130.589 917.065 L136.469 917.065 L136.469 939.588 L141.399 939.588 L141.399 943.477 L136.469 943.477 L136.469 951.625 L131.816 951.625 L131.816 943.477 L116.214 943.477 L116.214 938.963 L130.589 917.065 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M159.131 920.144 Q155.52 920.144 153.691 923.709 Q151.886 927.25 151.886 934.38 Q151.886 941.486 153.691 945.051 Q155.52 948.593 159.131 948.593 Q162.765 948.593 164.571 945.051 Q166.399 941.486 166.399 934.38 Q166.399 927.25 164.571 923.709 Q162.765 920.144 159.131 920.144 M159.131 916.44 Q164.941 916.44 167.997 921.047 Q171.075 925.63 171.075 934.38 Q171.075 943.107 167.997 947.713 Q164.941 952.296 159.131 952.296 Q153.321 952.296 150.242 947.713 Q147.186 943.107 147.186 934.38 Q147.186 925.63 150.242 921.047 Q153.321 916.44 159.131 916.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M189.293 920.144 Q185.682 920.144 183.853 923.709 Q182.047 927.25 182.047 934.38 Q182.047 941.486 183.853 945.051 Q185.682 948.593 189.293 948.593 Q192.927 948.593 194.733 945.051 Q196.561 941.486 196.561 934.38 Q196.561 927.25 194.733 923.709 Q192.927 920.144 189.293 920.144 M189.293 916.44 Q195.103 916.44 198.158 921.047 Q201.237 925.63 201.237 934.38 Q201.237 943.107 198.158 947.713 Q195.103 952.296 189.293 952.296 Q183.483 952.296 180.404 947.713 Q177.348 943.107 177.348 934.38 Q177.348 925.63 180.404 921.047 Q183.483 916.44 189.293 916.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M219.455 920.144 Q215.844 920.144 214.015 923.709 Q212.209 927.25 212.209 934.38 Q212.209 941.486 214.015 945.051 Q215.844 948.593 219.455 948.593 Q223.089 948.593 224.894 945.051 Q226.723 941.486 226.723 934.38 Q226.723 927.25 224.894 923.709 Q223.089 920.144 219.455 920.144 M219.455 916.44 Q225.265 916.44 228.32 921.047 Q231.399 925.63 231.399 934.38 Q231.399 943.107 228.32 947.713 Q225.265 952.296 219.455 952.296 Q213.644 952.296 210.566 947.713 Q207.51 943.107 207.51 934.38 Q207.51 925.63 210.566 921.047 Q213.644 916.44 219.455 916.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M129.548 539.176 Q126.4 539.176 124.548 541.329 Q122.719 543.481 122.719 547.231 Q122.719 550.958 124.548 553.134 Q126.4 555.287 129.548 555.287 Q132.696 555.287 134.525 553.134 Q136.376 550.958 136.376 547.231 Q136.376 543.481 134.525 541.329 Q132.696 539.176 129.548 539.176 M138.83 524.523 L138.83 528.782 Q137.071 527.949 135.265 527.509 Q133.483 527.07 131.724 527.07 Q127.094 527.07 124.64 530.195 Q122.21 533.32 121.863 539.639 Q123.228 537.625 125.288 536.56 Q127.349 535.472 129.825 535.472 Q135.034 535.472 138.043 538.644 Q141.075 541.792 141.075 547.231 Q141.075 552.556 137.927 555.773 Q134.779 558.991 129.548 558.991 Q123.552 558.991 120.381 554.407 Q117.21 549.801 117.21 541.074 Q117.21 532.88 121.099 528.019 Q124.988 523.134 131.538 523.134 Q133.298 523.134 135.08 523.482 Q136.886 523.829 138.83 524.523 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M159.131 526.838 Q155.52 526.838 153.691 530.403 Q151.886 533.945 151.886 541.074 Q151.886 548.181 153.691 551.745 Q155.52 555.287 159.131 555.287 Q162.765 555.287 164.571 551.745 Q166.399 548.181 166.399 541.074 Q166.399 533.945 164.571 530.403 Q162.765 526.838 159.131 526.838 M159.131 523.134 Q164.941 523.134 167.997 527.741 Q171.075 532.324 171.075 541.074 Q171.075 549.801 167.997 554.407 Q164.941 558.991 159.131 558.991 Q153.321 558.991 150.242 554.407 Q147.186 549.801 147.186 541.074 Q147.186 532.324 150.242 527.741 Q153.321 523.134 159.131 523.134 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M189.293 526.838 Q185.682 526.838 183.853 530.403 Q182.047 533.945 182.047 541.074 Q182.047 548.181 183.853 551.745 Q185.682 555.287 189.293 555.287 Q192.927 555.287 194.733 551.745 Q196.561 548.181 196.561 541.074 Q196.561 533.945 194.733 530.403 Q192.927 526.838 189.293 526.838 M189.293 523.134 Q195.103 523.134 198.158 527.741 Q201.237 532.324 201.237 541.074 Q201.237 549.801 198.158 554.407 Q195.103 558.991 189.293 558.991 Q183.483 558.991 180.404 554.407 Q177.348 549.801 177.348 541.074 Q177.348 532.324 180.404 527.741 Q183.483 523.134 189.293 523.134 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M219.455 526.838 Q215.844 526.838 214.015 530.403 Q212.209 533.945 212.209 541.074 Q212.209 548.181 214.015 551.745 Q215.844 555.287 219.455 555.287 Q223.089 555.287 224.894 551.745 Q226.723 548.181 226.723 541.074 Q226.723 533.945 224.894 530.403 Q223.089 526.838 219.455 526.838 M219.455 523.134 Q225.265 523.134 228.32 527.741 Q231.399 532.324 231.399 541.074 Q231.399 549.801 228.32 554.407 Q225.265 558.991 219.455 558.991 Q213.644 558.991 210.566 554.407 Q207.51 549.801 207.51 541.074 Q207.51 532.324 210.566 527.741 Q213.644 523.134 219.455 523.134 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M128.969 148.602 Q125.636 148.602 123.714 150.384 Q121.816 152.167 121.816 155.292 Q121.816 158.417 123.714 160.199 Q125.636 161.981 128.969 161.981 Q132.302 161.981 134.224 160.199 Q136.145 158.393 136.145 155.292 Q136.145 152.167 134.224 150.384 Q132.325 148.602 128.969 148.602 M124.293 146.611 Q121.284 145.87 119.594 143.81 Q117.927 141.75 117.927 138.787 Q117.927 134.643 120.867 132.236 Q123.83 129.829 128.969 129.829 Q134.131 129.829 137.071 132.236 Q140.011 134.643 140.011 138.787 Q140.011 141.75 138.321 143.81 Q136.654 145.87 133.668 146.611 Q137.048 147.398 138.923 149.69 Q140.821 151.981 140.821 155.292 Q140.821 160.315 137.742 163 Q134.687 165.685 128.969 165.685 Q123.251 165.685 120.173 163 Q117.117 160.315 117.117 155.292 Q117.117 151.981 119.015 149.69 Q120.913 147.398 124.293 146.611 M122.58 139.227 Q122.58 141.912 124.247 143.417 Q125.937 144.921 128.969 144.921 Q131.978 144.921 133.668 143.417 Q135.381 141.912 135.381 139.227 Q135.381 136.542 133.668 135.037 Q131.978 133.532 128.969 133.532 Q125.937 133.532 124.247 135.037 Q122.58 136.542 122.58 139.227 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M159.131 133.532 Q155.52 133.532 153.691 137.097 Q151.886 140.639 151.886 147.768 Q151.886 154.875 153.691 158.44 Q155.52 161.981 159.131 161.981 Q162.765 161.981 164.571 158.44 Q166.399 154.875 166.399 147.768 Q166.399 140.639 164.571 137.097 Q162.765 133.532 159.131 133.532 M159.131 129.829 Q164.941 129.829 167.997 134.435 Q171.075 139.018 171.075 147.768 Q171.075 156.495 167.997 161.102 Q164.941 165.685 159.131 165.685 Q153.321 165.685 150.242 161.102 Q147.186 156.495 147.186 147.768 Q147.186 139.018 150.242 134.435 Q153.321 129.829 159.131 129.829 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M189.293 133.532 Q185.682 133.532 183.853 137.097 Q182.047 140.639 182.047 147.768 Q182.047 154.875 183.853 158.44 Q185.682 161.981 189.293 161.981 Q192.927 161.981 194.733 158.44 Q196.561 154.875 196.561 147.768 Q196.561 140.639 194.733 137.097 Q192.927 133.532 189.293 133.532 M189.293 129.829 Q195.103 129.829 198.158 134.435 Q201.237 139.018 201.237 147.768 Q201.237 156.495 198.158 161.102 Q195.103 165.685 189.293 165.685 Q183.483 165.685 180.404 161.102 Q177.348 156.495 177.348 147.768 Q177.348 139.018 180.404 134.435 Q183.483 129.829 189.293 129.829 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M219.455 133.532 Q215.844 133.532 214.015 137.097 Q212.209 140.639 212.209 147.768 Q212.209 154.875 214.015 158.44 Q215.844 161.981 219.455 161.981 Q223.089 161.981 224.894 158.44 Q226.723 154.875 226.723 147.768 Q226.723 140.639 224.894 137.097 Q223.089 133.532 219.455 133.532 M219.455 129.829 Q225.265 129.829 228.32 134.435 Q231.399 139.018 231.399 147.768 Q231.399 156.495 228.32 161.102 Q225.265 165.685 219.455 165.685 Q213.644 165.685 210.566 161.102 Q207.51 156.495 207.51 147.768 Q207.51 139.018 210.566 134.435 Q213.644 129.829 219.455 129.829 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M17.7787 939.959 L24.5582 939.959 Q21.5345 943.206 20.0386 946.898 Q18.5426 950.558 18.5426 954.696 Q18.5426 962.844 23.5397 967.173 Q28.5049 971.501 37.9262 971.501 Q47.3156 971.501 52.3127 967.173 Q57.2779 962.844 57.2779 954.696 Q57.2779 950.558 55.782 946.898 Q54.2861 943.206 51.2623 939.959 L57.9782 939.959 Q60.2698 943.333 61.4156 947.121 Q62.5615 950.877 62.5615 955.078 Q62.5615 965.868 55.973 972.074 Q49.3526 978.281 37.9262 978.281 Q26.4679 978.281 19.8794 972.074 Q13.2591 965.868 13.2591 955.078 Q13.2591 950.813 14.4049 947.057 Q15.5189 943.269 17.7787 939.959 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M30.0964 916.47 Q30.0964 921.18 33.7885 923.918 Q37.4488 926.655 43.8463 926.655 Q50.2438 926.655 53.9359 923.95 Q57.5962 921.212 57.5962 916.47 Q57.5962 911.791 53.9041 909.054 Q50.212 906.317 43.8463 906.317 Q37.5124 906.317 33.8203 909.054 Q30.0964 911.791 30.0964 916.47 M25.1311 916.47 Q25.1311 908.831 30.0964 904.471 Q35.0616 900.11 43.8463 900.11 Q52.5991 900.11 57.5962 904.471 Q62.5615 908.831 62.5615 916.47 Q62.5615 924.141 57.5962 928.501 Q52.5991 932.83 43.8463 932.83 Q35.0616 932.83 30.0964 928.501 Q25.1311 924.141 25.1311 916.47 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M47.5702 891.007 L25.9905 891.007 L25.9905 885.151 L47.3474 885.151 Q52.4082 885.151 54.9545 883.177 Q57.4689 881.204 57.4689 877.257 Q57.4689 872.515 54.4452 869.777 Q51.4215 867.008 46.2016 867.008 L25.9905 867.008 L25.9905 861.152 L61.6384 861.152 L61.6384 867.008 L56.1639 867.008 Q59.4104 869.141 61.0019 871.974 Q62.5615 874.774 62.5615 878.498 Q62.5615 884.641 58.742 887.824 Q54.9226 891.007 47.5702 891.007 M25.1311 876.27 L25.1311 876.27 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M40.1224 819.457 L61.6384 819.457 L61.6384 825.313 L40.3133 825.313 Q35.2526 825.313 32.7381 827.286 Q30.2237 829.26 30.2237 833.206 Q30.2237 837.949 33.2474 840.686 Q36.2711 843.423 41.491 843.423 L61.6384 843.423 L61.6384 849.312 L25.9905 849.312 L25.9905 843.423 L31.5287 843.423 Q28.314 841.323 26.7225 838.49 Q25.1311 835.625 25.1311 831.901 Q25.1311 825.759 28.9505 822.608 Q32.7381 819.457 40.1224 819.457 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M15.869 801.983 L25.9905 801.983 L25.9905 789.92 L30.542 789.92 L30.542 801.983 L49.8937 801.983 Q54.2542 801.983 55.4955 800.805 Q56.7368 799.595 56.7368 795.935 L56.7368 789.92 L61.6384 789.92 L61.6384 795.935 Q61.6384 802.715 59.124 805.293 Q56.5777 807.871 49.8937 807.871 L30.542 807.871 L30.542 812.168 L25.9905 812.168 L25.9905 807.871 L15.869 807.871 L15.869 801.983 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip322)" d="M402.02 47.2441 L402.02 1720.96 L402.302 1720.96 L402.302 47.2441 L402.02 47.2441 L402.02 47.2441  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="402.02,47.2441 402.02,1720.96 402.302,1720.96 402.302,47.2441 402.02,47.2441 "/>
<path clip-path="url(#clip322)" d="M402.302 1720.96 L402.302 1720.96 L402.584 1720.96 L402.584 1720.96 L402.302 1720.96 L402.302 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="402.302,1720.96 402.302,1720.96 402.584,1720.96 402.302,1720.96 "/>
<path clip-path="url(#clip322)" d="M402.584 1720.96 L402.584 1720.96 L402.865 1720.96 L402.865 1720.96 L402.584 1720.96 L402.584 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="402.584,1720.96 402.584,1720.96 402.865,1720.96 402.584,1720.96 "/>
<path clip-path="url(#clip322)" d="M402.865 1720.96 L402.865 1720.96 L403.147 1720.96 L403.147 1720.96 L402.865 1720.96 L402.865 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="402.865,1720.96 402.865,1720.96 403.147,1720.96 402.865,1720.96 "/>
<path clip-path="url(#clip322)" d="M403.147 1720.96 L403.147 1720.96 L403.429 1720.96 L403.429 1720.96 L403.147 1720.96 L403.147 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="403.147,1720.96 403.147,1720.96 403.429,1720.96 403.147,1720.96 "/>
<path clip-path="url(#clip322)" d="M403.429 1720.96 L403.429 1720.96 L403.711 1720.96 L403.711 1720.96 L403.429 1720.96 L403.429 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="403.429,1720.96 403.429,1720.96 403.711,1720.96 403.429,1720.96 "/>
<path clip-path="url(#clip322)" d="M403.711 1720.96 L403.711 1720.96 L403.992 1720.96 L403.992 1720.96 L403.711 1720.96 L403.711 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="403.711,1720.96 403.711,1720.96 403.992,1720.96 403.711,1720.96 "/>
<path clip-path="url(#clip322)" d="M403.992 1720.96 L403.992 1720.96 L404.274 1720.96 L404.274 1720.96 L403.992 1720.96 L403.992 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="403.992,1720.96 403.992,1720.96 404.274,1720.96 403.992,1720.96 "/>
<path clip-path="url(#clip322)" d="M404.274 1720.96 L404.274 1720.96 L404.556 1720.96 L404.556 1720.96 L404.274 1720.96 L404.274 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="404.274,1720.96 404.274,1720.96 404.556,1720.96 404.274,1720.96 "/>
<path clip-path="url(#clip322)" d="M404.556 1720.96 L404.556 1720.96 L404.838 1720.96 L404.838 1720.96 L404.556 1720.96 L404.556 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="404.556,1720.96 404.556,1720.96 404.838,1720.96 404.556,1720.96 "/>
<path clip-path="url(#clip322)" d="M404.838 1720.96 L404.838 1720.96 L405.119 1720.96 L405.119 1720.96 L404.838 1720.96 L404.838 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="404.838,1720.96 404.838,1720.96 405.119,1720.96 404.838,1720.96 "/>
<path clip-path="url(#clip322)" d="M405.119 1720.96 L405.119 1720.96 L405.401 1720.96 L405.401 1720.96 L405.119 1720.96 L405.119 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="405.119,1720.96 405.119,1720.96 405.401,1720.96 405.119,1720.96 "/>
<path clip-path="url(#clip322)" d="M405.401 1720.96 L405.401 1720.96 L405.683 1720.96 L405.683 1720.96 L405.401 1720.96 L405.401 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="405.401,1720.96 405.401,1720.96 405.683,1720.96 405.401,1720.96 "/>
<path clip-path="url(#clip322)" d="M405.683 1720.96 L405.683 1720.96 L405.964 1720.96 L405.964 1720.96 L405.683 1720.96 L405.683 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="405.683,1720.96 405.683,1720.96 405.964,1720.96 405.683,1720.96 "/>
<path clip-path="url(#clip322)" d="M405.964 1720.96 L405.964 1720.96 L406.246 1720.96 L406.246 1720.96 L405.964 1720.96 L405.964 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="405.964,1720.96 405.964,1720.96 406.246,1720.96 405.964,1720.96 "/>
<path clip-path="url(#clip322)" d="M406.246 1720.96 L406.246 1720.96 L406.528 1720.96 L406.528 1720.96 L406.246 1720.96 L406.246 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="406.246,1720.96 406.246,1720.96 406.528,1720.96 406.246,1720.96 "/>
<path clip-path="url(#clip322)" d="M406.528 1720.96 L406.528 1720.96 L406.81 1720.96 L406.81 1720.96 L406.528 1720.96 L406.528 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="406.528,1720.96 406.528,1720.96 406.81,1720.96 406.528,1720.96 "/>
<path clip-path="url(#clip322)" d="M406.81 1720.96 L406.81 1720.96 L407.091 1720.96 L407.091 1720.96 L406.81 1720.96 L406.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="406.81,1720.96 406.81,1720.96 407.091,1720.96 406.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M407.091 1720.96 L407.091 1720.96 L407.373 1720.96 L407.373 1720.96 L407.091 1720.96 L407.091 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="407.091,1720.96 407.091,1720.96 407.373,1720.96 407.091,1720.96 "/>
<path clip-path="url(#clip322)" d="M407.373 1720.96 L407.373 1720.96 L407.655 1720.96 L407.655 1720.96 L407.373 1720.96 L407.373 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="407.373,1720.96 407.373,1720.96 407.655,1720.96 407.373,1720.96 "/>
<path clip-path="url(#clip322)" d="M407.655 1720.96 L407.655 1720.96 L407.936 1720.96 L407.936 1720.96 L407.655 1720.96 L407.655 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="407.655,1720.96 407.655,1720.96 407.936,1720.96 407.655,1720.96 "/>
<path clip-path="url(#clip322)" d="M407.936 1720.96 L407.936 1720.96 L408.218 1720.96 L408.218 1720.96 L407.936 1720.96 L407.936 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="407.936,1720.96 407.936,1720.96 408.218,1720.96 407.936,1720.96 "/>
<path clip-path="url(#clip322)" d="M408.218 1720.96 L408.218 1720.96 L408.5 1720.96 L408.5 1720.96 L408.218 1720.96 L408.218 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="408.218,1720.96 408.218,1720.96 408.5,1720.96 408.218,1720.96 "/>
<path clip-path="url(#clip322)" d="M408.5 1720.96 L408.5 1720.96 L408.782 1720.96 L408.782 1720.96 L408.5 1720.96 L408.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="408.5,1720.96 408.5,1720.96 408.782,1720.96 408.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M408.782 1720.96 L408.782 1720.96 L409.063 1720.96 L409.063 1720.96 L408.782 1720.96 L408.782 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="408.782,1720.96 408.782,1720.96 409.063,1720.96 408.782,1720.96 "/>
<path clip-path="url(#clip322)" d="M409.063 1720.96 L409.063 1720.96 L409.345 1720.96 L409.345 1720.96 L409.063 1720.96 L409.063 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="409.063,1720.96 409.063,1720.96 409.345,1720.96 409.063,1720.96 "/>
<path clip-path="url(#clip322)" d="M409.345 1720.96 L409.345 1720.96 L409.627 1720.96 L409.627 1720.96 L409.345 1720.96 L409.345 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="409.345,1720.96 409.345,1720.96 409.627,1720.96 409.345,1720.96 "/>
<path clip-path="url(#clip322)" d="M409.627 1720.96 L409.627 1720.96 L409.909 1720.96 L409.909 1720.96 L409.627 1720.96 L409.627 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="409.627,1720.96 409.627,1720.96 409.909,1720.96 409.627,1720.96 "/>
<path clip-path="url(#clip322)" d="M409.909 1720.96 L409.909 1720.96 L410.19 1720.96 L410.19 1720.96 L409.909 1720.96 L409.909 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="409.909,1720.96 409.909,1720.96 410.19,1720.96 409.909,1720.96 "/>
<path clip-path="url(#clip322)" d="M410.19 1720.96 L410.19 1720.96 L410.472 1720.96 L410.472 1720.96 L410.19 1720.96 L410.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="410.19,1720.96 410.19,1720.96 410.472,1720.96 410.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M410.472 1720.96 L410.472 1720.96 L410.754 1720.96 L410.754 1720.96 L410.472 1720.96 L410.472 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="410.472,1720.96 410.472,1720.96 410.754,1720.96 410.472,1720.96 "/>
<path clip-path="url(#clip322)" d="M410.754 1720.96 L410.754 1720.96 L411.035 1720.96 L411.035 1720.96 L410.754 1720.96 L410.754 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="410.754,1720.96 410.754,1720.96 411.035,1720.96 410.754,1720.96 "/>
<path clip-path="url(#clip322)" d="M411.035 1720.96 L411.035 1720.96 L411.317 1720.96 L411.317 1720.96 L411.035 1720.96 L411.035 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="411.035,1720.96 411.035,1720.96 411.317,1720.96 411.035,1720.96 "/>
<path clip-path="url(#clip322)" d="M411.317 1720.96 L411.317 1720.96 L411.599 1720.96 L411.599 1720.96 L411.317 1720.96 L411.317 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="411.317,1720.96 411.317,1720.96 411.599,1720.96 411.317,1720.96 "/>
<path clip-path="url(#clip322)" d="M411.599 1720.96 L411.599 1720.96 L411.881 1720.96 L411.881 1720.96 L411.599 1720.96 L411.599 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="411.599,1720.96 411.599,1720.96 411.881,1720.96 411.599,1720.96 "/>
<path clip-path="url(#clip322)" d="M411.881 1720.96 L411.881 1720.96 L412.162 1720.96 L412.162 1720.96 L411.881 1720.96 L411.881 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="411.881,1720.96 411.881,1720.96 412.162,1720.96 411.881,1720.96 "/>
<path clip-path="url(#clip322)" d="M412.162 1720.96 L412.162 1720.96 L412.444 1720.96 L412.444 1720.96 L412.162 1720.96 L412.162 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="412.162,1720.96 412.162,1720.96 412.444,1720.96 412.162,1720.96 "/>
<path clip-path="url(#clip322)" d="M412.444 1720.96 L412.444 1720.96 L412.726 1720.96 L412.726 1720.96 L412.444 1720.96 L412.444 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="412.444,1720.96 412.444,1720.96 412.726,1720.96 412.444,1720.96 "/>
<path clip-path="url(#clip322)" d="M412.726 1720.96 L412.726 1720.96 L413.008 1720.96 L413.008 1720.96 L412.726 1720.96 L412.726 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="412.726,1720.96 412.726,1720.96 413.008,1720.96 412.726,1720.96 "/>
<path clip-path="url(#clip322)" d="M413.008 1720.96 L413.008 1720.96 L413.289 1720.96 L413.289 1720.96 L413.008 1720.96 L413.008 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="413.008,1720.96 413.008,1720.96 413.289,1720.96 413.008,1720.96 "/>
<path clip-path="url(#clip322)" d="M413.289 1720.96 L413.289 1720.96 L413.571 1720.96 L413.571 1720.96 L413.289 1720.96 L413.289 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="413.289,1720.96 413.289,1720.96 413.571,1720.96 413.289,1720.96 "/>
<path clip-path="url(#clip322)" d="M413.571 1720.96 L413.571 1720.96 L413.853 1720.96 L413.853 1720.96 L413.571 1720.96 L413.571 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="413.571,1720.96 413.571,1720.96 413.853,1720.96 413.571,1720.96 "/>
<path clip-path="url(#clip322)" d="M413.853 1720.96 L413.853 1720.96 L414.134 1720.96 L414.134 1720.96 L413.853 1720.96 L413.853 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="413.853,1720.96 413.853,1720.96 414.134,1720.96 413.853,1720.96 "/>
<path clip-path="url(#clip322)" d="M414.134 1720.96 L414.134 1720.96 L414.416 1720.96 L414.416 1720.96 L414.134 1720.96 L414.134 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="414.134,1720.96 414.134,1720.96 414.416,1720.96 414.134,1720.96 "/>
<path clip-path="url(#clip322)" d="M414.416 1720.96 L414.416 1720.96 L414.698 1720.96 L414.698 1720.96 L414.416 1720.96 L414.416 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="414.416,1720.96 414.416,1720.96 414.698,1720.96 414.416,1720.96 "/>
<path clip-path="url(#clip322)" d="M414.698 1720.96 L414.698 1720.96 L414.98 1720.96 L414.98 1720.96 L414.698 1720.96 L414.698 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="414.698,1720.96 414.698,1720.96 414.98,1720.96 414.698,1720.96 "/>
<path clip-path="url(#clip322)" d="M414.98 1720.96 L414.98 1720.96 L415.261 1720.96 L415.261 1720.96 L414.98 1720.96 L414.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="414.98,1720.96 414.98,1720.96 415.261,1720.96 414.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M415.261 1720.96 L415.261 1720.96 L415.543 1720.96 L415.543 1720.96 L415.261 1720.96 L415.261 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="415.261,1720.96 415.261,1720.96 415.543,1720.96 415.261,1720.96 "/>
<path clip-path="url(#clip322)" d="M415.543 1720.96 L415.543 1720.96 L415.825 1720.96 L415.825 1720.96 L415.543 1720.96 L415.543 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="415.543,1720.96 415.543,1720.96 415.825,1720.96 415.543,1720.96 "/>
<path clip-path="url(#clip322)" d="M415.825 1720.96 L415.825 1720.96 L416.107 1720.96 L416.107 1720.96 L415.825 1720.96 L415.825 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="415.825,1720.96 415.825,1720.96 416.107,1720.96 415.825,1720.96 "/>
<path clip-path="url(#clip322)" d="M416.107 1720.96 L416.107 1720.96 L416.388 1720.96 L416.388 1720.96 L416.107 1720.96 L416.107 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="416.107,1720.96 416.107,1720.96 416.388,1720.96 416.107,1720.96 "/>
<path clip-path="url(#clip322)" d="M416.388 1720.96 L416.388 1720.96 L416.67 1720.96 L416.67 1720.96 L416.388 1720.96 L416.388 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="416.388,1720.96 416.388,1720.96 416.67,1720.96 416.388,1720.96 "/>
<path clip-path="url(#clip322)" d="M416.67 1720.96 L416.67 1720.96 L416.952 1720.96 L416.952 1720.96 L416.67 1720.96 L416.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="416.67,1720.96 416.67,1720.96 416.952,1720.96 416.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M416.952 1720.96 L416.952 1720.96 L417.233 1720.96 L417.233 1720.96 L416.952 1720.96 L416.952 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="416.952,1720.96 416.952,1720.96 417.233,1720.96 416.952,1720.96 "/>
<path clip-path="url(#clip322)" d="M417.233 1720.96 L417.233 1720.96 L417.515 1720.96 L417.515 1720.96 L417.233 1720.96 L417.233 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="417.233,1720.96 417.233,1720.96 417.515,1720.96 417.233,1720.96 "/>
<path clip-path="url(#clip322)" d="M417.515 1720.96 L417.515 1720.96 L417.797 1720.96 L417.797 1720.96 L417.515 1720.96 L417.515 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="417.515,1720.96 417.515,1720.96 417.797,1720.96 417.515,1720.96 "/>
<path clip-path="url(#clip322)" d="M417.797 1720.96 L417.797 1720.96 L418.079 1720.96 L418.079 1720.96 L417.797 1720.96 L417.797 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="417.797,1720.96 417.797,1720.96 418.079,1720.96 417.797,1720.96 "/>
<path clip-path="url(#clip322)" d="M418.079 1720.96 L418.079 1720.96 L418.36 1720.96 L418.36 1720.96 L418.079 1720.96 L418.079 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="418.079,1720.96 418.079,1720.96 418.36,1720.96 418.079,1720.96 "/>
<path clip-path="url(#clip322)" d="M418.36 1720.96 L418.36 1720.96 L418.642 1720.96 L418.642 1720.96 L418.36 1720.96 L418.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="418.36,1720.96 418.36,1720.96 418.642,1720.96 418.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M418.642 1720.96 L418.642 1720.96 L418.924 1720.96 L418.924 1720.96 L418.642 1720.96 L418.642 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="418.642,1720.96 418.642,1720.96 418.924,1720.96 418.642,1720.96 "/>
<path clip-path="url(#clip322)" d="M418.924 1720.96 L418.924 1720.96 L419.206 1720.96 L419.206 1720.96 L418.924 1720.96 L418.924 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="418.924,1720.96 418.924,1720.96 419.206,1720.96 418.924,1720.96 "/>
<path clip-path="url(#clip322)" d="M419.206 1720.96 L419.206 1720.96 L419.487 1720.96 L419.487 1720.96 L419.206 1720.96 L419.206 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="419.206,1720.96 419.206,1720.96 419.487,1720.96 419.206,1720.96 "/>
<path clip-path="url(#clip322)" d="M419.487 1720.96 L419.487 1720.96 L419.769 1720.96 L419.769 1720.96 L419.487 1720.96 L419.487 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="419.487,1720.96 419.487,1720.96 419.769,1720.96 419.487,1720.96 "/>
<path clip-path="url(#clip322)" d="M419.769 1720.96 L419.769 1720.96 L420.051 1720.96 L420.051 1720.96 L419.769 1720.96 L419.769 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="419.769,1720.96 419.769,1720.96 420.051,1720.96 419.769,1720.96 "/>
<path clip-path="url(#clip322)" d="M420.051 1720.96 L420.051 1720.96 L420.332 1720.96 L420.332 1720.96 L420.051 1720.96 L420.051 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="420.051,1720.96 420.051,1720.96 420.332,1720.96 420.051,1720.96 "/>
<path clip-path="url(#clip322)" d="M420.332 1720.96 L420.332 1720.96 L420.614 1720.96 L420.614 1720.96 L420.332 1720.96 L420.332 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="420.332,1720.96 420.332,1720.96 420.614,1720.96 420.332,1720.96 "/>
<path clip-path="url(#clip322)" d="M420.614 1720.96 L420.614 1720.96 L420.896 1720.96 L420.896 1720.96 L420.614 1720.96 L420.614 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="420.614,1720.96 420.614,1720.96 420.896,1720.96 420.614,1720.96 "/>
<path clip-path="url(#clip322)" d="M420.896 1720.96 L420.896 1720.96 L421.178 1720.96 L421.178 1720.96 L420.896 1720.96 L420.896 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="420.896,1720.96 420.896,1720.96 421.178,1720.96 420.896,1720.96 "/>
<path clip-path="url(#clip322)" d="M421.178 1720.96 L421.178 1720.96 L421.459 1720.96 L421.459 1720.96 L421.178 1720.96 L421.178 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="421.178,1720.96 421.178,1720.96 421.459,1720.96 421.178,1720.96 "/>
<path clip-path="url(#clip322)" d="M421.459 1720.96 L421.459 1720.96 L421.741 1720.96 L421.741 1720.96 L421.459 1720.96 L421.459 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="421.459,1720.96 421.459,1720.96 421.741,1720.96 421.459,1720.96 "/>
<path clip-path="url(#clip322)" d="M421.741 1720.96 L421.741 1720.96 L422.023 1720.96 L422.023 1720.96 L421.741 1720.96 L421.741 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="421.741,1720.96 421.741,1720.96 422.023,1720.96 421.741,1720.96 "/>
<path clip-path="url(#clip322)" d="M422.023 1720.96 L422.023 1720.96 L422.305 1720.96 L422.305 1720.96 L422.023 1720.96 L422.023 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="422.023,1720.96 422.023,1720.96 422.305,1720.96 422.023,1720.96 "/>
<path clip-path="url(#clip322)" d="M422.305 1720.96 L422.305 1720.96 L422.586 1720.96 L422.586 1720.96 L422.305 1720.96 L422.305 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="422.305,1720.96 422.305,1720.96 422.586,1720.96 422.305,1720.96 "/>
<path clip-path="url(#clip322)" d="M422.586 1720.96 L422.586 1720.96 L422.868 1720.96 L422.868 1720.96 L422.586 1720.96 L422.586 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="422.586,1720.96 422.586,1720.96 422.868,1720.96 422.586,1720.96 "/>
<path clip-path="url(#clip322)" d="M422.868 1720.96 L422.868 1720.96 L423.15 1720.96 L423.15 1720.96 L422.868 1720.96 L422.868 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="422.868,1720.96 422.868,1720.96 423.15,1720.96 422.868,1720.96 "/>
<path clip-path="url(#clip322)" d="M423.15 1720.96 L423.15 1720.96 L423.431 1720.96 L423.431 1720.96 L423.15 1720.96 L423.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="423.15,1720.96 423.15,1720.96 423.431,1720.96 423.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M423.431 1720.96 L423.431 1720.96 L423.713 1720.96 L423.713 1720.96 L423.431 1720.96 L423.431 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="423.431,1720.96 423.431,1720.96 423.713,1720.96 423.431,1720.96 "/>
<path clip-path="url(#clip322)" d="M423.713 1720.96 L423.713 1720.96 L423.995 1720.96 L423.995 1720.96 L423.713 1720.96 L423.713 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="423.713,1720.96 423.713,1720.96 423.995,1720.96 423.713,1720.96 "/>
<path clip-path="url(#clip322)" d="M423.995 1720.96 L423.995 1720.96 L424.277 1720.96 L424.277 1720.96 L423.995 1720.96 L423.995 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="423.995,1720.96 423.995,1720.96 424.277,1720.96 423.995,1720.96 "/>
<path clip-path="url(#clip322)" d="M424.277 1720.96 L424.277 1720.96 L424.558 1720.96 L424.558 1720.96 L424.277 1720.96 L424.277 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="424.277,1720.96 424.277,1720.96 424.558,1720.96 424.277,1720.96 "/>
<path clip-path="url(#clip322)" d="M424.558 1720.96 L424.558 1720.96 L424.84 1720.96 L424.84 1720.96 L424.558 1720.96 L424.558 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="424.558,1720.96 424.558,1720.96 424.84,1720.96 424.558,1720.96 "/>
<path clip-path="url(#clip322)" d="M424.84 1720.96 L424.84 1720.96 L425.122 1720.96 L425.122 1720.96 L424.84 1720.96 L424.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="424.84,1720.96 424.84,1720.96 425.122,1720.96 424.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M425.122 1720.96 L425.122 1720.96 L425.403 1720.96 L425.403 1720.96 L425.122 1720.96 L425.122 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="425.122,1720.96 425.122,1720.96 425.403,1720.96 425.122,1720.96 "/>
<path clip-path="url(#clip322)" d="M425.403 1720.96 L425.403 1720.96 L425.685 1720.96 L425.685 1720.96 L425.403 1720.96 L425.403 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="425.403,1720.96 425.403,1720.96 425.685,1720.96 425.403,1720.96 "/>
<path clip-path="url(#clip322)" d="M425.685 1720.96 L425.685 1720.96 L425.967 1720.96 L425.967 1720.96 L425.685 1720.96 L425.685 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="425.685,1720.96 425.685,1720.96 425.967,1720.96 425.685,1720.96 "/>
<path clip-path="url(#clip322)" d="M425.967 1720.96 L425.967 1720.96 L426.249 1720.96 L426.249 1720.96 L425.967 1720.96 L425.967 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="425.967,1720.96 425.967,1720.96 426.249,1720.96 425.967,1720.96 "/>
<path clip-path="url(#clip322)" d="M426.249 1720.96 L426.249 1720.96 L426.53 1720.96 L426.53 1720.96 L426.249 1720.96 L426.249 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="426.249,1720.96 426.249,1720.96 426.53,1720.96 426.249,1720.96 "/>
<path clip-path="url(#clip322)" d="M426.53 1720.96 L426.53 1720.96 L426.812 1720.96 L426.812 1720.96 L426.53 1720.96 L426.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="426.53,1720.96 426.53,1720.96 426.812,1720.96 426.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M426.812 1720.96 L426.812 1720.96 L427.094 1720.96 L427.094 1720.96 L426.812 1720.96 L426.812 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="426.812,1720.96 426.812,1720.96 427.094,1720.96 426.812,1720.96 "/>
<path clip-path="url(#clip322)" d="M427.094 1720.96 L427.094 1720.96 L427.376 1720.96 L427.376 1720.96 L427.094 1720.96 L427.094 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="427.094,1720.96 427.094,1720.96 427.376,1720.96 427.094,1720.96 "/>
<path clip-path="url(#clip322)" d="M427.376 1720.96 L427.376 1720.96 L427.657 1720.96 L427.657 1720.96 L427.376 1720.96 L427.376 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="427.376,1720.96 427.376,1720.96 427.657,1720.96 427.376,1720.96 "/>
<path clip-path="url(#clip322)" d="M427.657 1720.96 L427.657 1720.96 L427.939 1720.96 L427.939 1720.96 L427.657 1720.96 L427.657 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="427.657,1720.96 427.657,1720.96 427.939,1720.96 427.657,1720.96 "/>
<path clip-path="url(#clip322)" d="M427.939 1720.96 L427.939 1720.96 L428.221 1720.96 L428.221 1720.96 L427.939 1720.96 L427.939 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="427.939,1720.96 427.939,1720.96 428.221,1720.96 427.939,1720.96 "/>
<path clip-path="url(#clip322)" d="M428.221 1720.96 L428.221 1720.96 L428.502 1720.96 L428.502 1720.96 L428.221 1720.96 L428.221 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="428.221,1720.96 428.221,1720.96 428.502,1720.96 428.221,1720.96 "/>
<path clip-path="url(#clip322)" d="M428.502 1720.96 L428.502 1720.96 L428.784 1720.96 L428.784 1720.96 L428.502 1720.96 L428.502 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="428.502,1720.96 428.502,1720.96 428.784,1720.96 428.502,1720.96 "/>
<path clip-path="url(#clip322)" d="M428.784 1720.96 L428.784 1720.96 L429.066 1720.96 L429.066 1720.96 L428.784 1720.96 L428.784 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="428.784,1720.96 428.784,1720.96 429.066,1720.96 428.784,1720.96 "/>
<path clip-path="url(#clip322)" d="M429.066 1720.96 L429.066 1720.96 L429.348 1720.96 L429.348 1720.96 L429.066 1720.96 L429.066 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="429.066,1720.96 429.066,1720.96 429.348,1720.96 429.066,1720.96 "/>
<path clip-path="url(#clip322)" d="M429.348 1720.96 L429.348 1720.96 L429.629 1720.96 L429.629 1720.96 L429.348 1720.96 L429.348 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="429.348,1720.96 429.348,1720.96 429.629,1720.96 429.348,1720.96 "/>
<path clip-path="url(#clip322)" d="M429.629 1720.96 L429.629 1720.96 L429.911 1720.96 L429.911 1720.96 L429.629 1720.96 L429.629 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="429.629,1720.96 429.629,1720.96 429.911,1720.96 429.629,1720.96 "/>
<path clip-path="url(#clip322)" d="M429.911 1720.96 L429.911 1720.96 L430.193 1720.96 L430.193 1720.96 L429.911 1720.96 L429.911 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="429.911,1720.96 429.911,1720.96 430.193,1720.96 429.911,1720.96 "/>
<path clip-path="url(#clip322)" d="M430.193 1720.96 L430.193 1720.96 L430.475 1720.96 L430.475 1720.96 L430.193 1720.96 L430.193 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="430.193,1720.96 430.193,1720.96 430.475,1720.96 430.193,1720.96 "/>
<path clip-path="url(#clip322)" d="M430.475 1720.96 L430.475 1720.96 L430.756 1720.96 L430.756 1720.96 L430.475 1720.96 L430.475 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="430.475,1720.96 430.475,1720.96 430.756,1720.96 430.475,1720.96 "/>
<path clip-path="url(#clip322)" d="M430.756 1720.96 L430.756 1720.96 L431.038 1720.96 L431.038 1720.96 L430.756 1720.96 L430.756 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="430.756,1720.96 430.756,1720.96 431.038,1720.96 430.756,1720.96 "/>
<path clip-path="url(#clip322)" d="M431.038 1720.96 L431.038 1720.96 L431.32 1720.96 L431.32 1720.96 L431.038 1720.96 L431.038 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="431.038,1720.96 431.038,1720.96 431.32,1720.96 431.038,1720.96 "/>
<path clip-path="url(#clip322)" d="M431.32 1720.96 L431.32 1720.96 L431.601 1720.96 L431.601 1720.96 L431.32 1720.96 L431.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="431.32,1720.96 431.32,1720.96 431.601,1720.96 431.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M431.601 1720.96 L431.601 1720.96 L431.883 1720.96 L431.883 1720.96 L431.601 1720.96 L431.601 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="431.601,1720.96 431.601,1720.96 431.883,1720.96 431.601,1720.96 "/>
<path clip-path="url(#clip322)" d="M431.883 1720.96 L431.883 1720.96 L432.165 1720.96 L432.165 1720.96 L431.883 1720.96 L431.883 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="431.883,1720.96 431.883,1720.96 432.165,1720.96 431.883,1720.96 "/>
<path clip-path="url(#clip322)" d="M432.165 1720.96 L432.165 1720.96 L432.447 1720.96 L432.447 1720.96 L432.165 1720.96 L432.165 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="432.165,1720.96 432.165,1720.96 432.447,1720.96 432.165,1720.96 "/>
<path clip-path="url(#clip322)" d="M432.447 1720.96 L432.447 1720.96 L432.728 1720.96 L432.728 1720.96 L432.447 1720.96 L432.447 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="432.447,1720.96 432.447,1720.96 432.728,1720.96 432.447,1720.96 "/>
<path clip-path="url(#clip322)" d="M432.728 1720.96 L432.728 1720.96 L433.01 1720.96 L433.01 1720.96 L432.728 1720.96 L432.728 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="432.728,1720.96 432.728,1720.96 433.01,1720.96 432.728,1720.96 "/>
<path clip-path="url(#clip322)" d="M433.01 1720.96 L433.01 1720.96 L433.292 1720.96 L433.292 1720.96 L433.01 1720.96 L433.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="433.01,1720.96 433.01,1720.96 433.292,1720.96 433.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M433.292 1720.96 L433.292 1720.96 L433.574 1720.96 L433.574 1720.96 L433.292 1720.96 L433.292 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="433.292,1720.96 433.292,1720.96 433.574,1720.96 433.292,1720.96 "/>
<path clip-path="url(#clip322)" d="M433.574 1720.96 L433.574 1720.96 L433.855 1720.96 L433.855 1720.96 L433.574 1720.96 L433.574 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="433.574,1720.96 433.574,1720.96 433.855,1720.96 433.574,1720.96 "/>
<path clip-path="url(#clip322)" d="M433.855 1720.96 L433.855 1720.96 L434.137 1720.96 L434.137 1720.96 L433.855 1720.96 L433.855 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="433.855,1720.96 433.855,1720.96 434.137,1720.96 433.855,1720.96 "/>
<path clip-path="url(#clip322)" d="M434.137 1720.96 L434.137 1720.96 L434.419 1720.96 L434.419 1720.96 L434.137 1720.96 L434.137 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="434.137,1720.96 434.137,1720.96 434.419,1720.96 434.137,1720.96 "/>
<path clip-path="url(#clip322)" d="M434.419 1720.96 L434.419 1720.96 L434.7 1720.96 L434.7 1720.96 L434.419 1720.96 L434.419 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="434.419,1720.96 434.419,1720.96 434.7,1720.96 434.419,1720.96 "/>
<path clip-path="url(#clip322)" d="M434.7 1720.96 L434.7 1720.96 L434.982 1720.96 L434.982 1720.96 L434.7 1720.96 L434.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="434.7,1720.96 434.7,1720.96 434.982,1720.96 434.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M434.982 1720.96 L434.982 1720.96 L435.264 1720.96 L435.264 1720.96 L434.982 1720.96 L434.982 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="434.982,1720.96 434.982,1720.96 435.264,1720.96 434.982,1720.96 "/>
<path clip-path="url(#clip322)" d="M435.264 1720.96 L435.264 1720.96 L435.546 1720.96 L435.546 1720.96 L435.264 1720.96 L435.264 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="435.264,1720.96 435.264,1720.96 435.546,1720.96 435.264,1720.96 "/>
<path clip-path="url(#clip322)" d="M435.546 1720.96 L435.546 1720.96 L435.827 1720.96 L435.827 1720.96 L435.546 1720.96 L435.546 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="435.546,1720.96 435.546,1720.96 435.827,1720.96 435.546,1720.96 "/>
<path clip-path="url(#clip322)" d="M435.827 1720.96 L435.827 1720.96 L436.109 1720.96 L436.109 1720.96 L435.827 1720.96 L435.827 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="435.827,1720.96 435.827,1720.96 436.109,1720.96 435.827,1720.96 "/>
<path clip-path="url(#clip322)" d="M436.109 1720.96 L436.109 1720.96 L436.391 1720.96 L436.391 1720.96 L436.109 1720.96 L436.109 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="436.109,1720.96 436.109,1720.96 436.391,1720.96 436.109,1720.96 "/>
<path clip-path="url(#clip322)" d="M436.391 1720.96 L436.391 1720.96 L436.673 1720.96 L436.673 1720.96 L436.391 1720.96 L436.391 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="436.391,1720.96 436.391,1720.96 436.673,1720.96 436.391,1720.96 "/>
<path clip-path="url(#clip322)" d="M436.673 1720.96 L436.673 1720.96 L436.954 1720.96 L436.954 1720.96 L436.673 1720.96 L436.673 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="436.673,1720.96 436.673,1720.96 436.954,1720.96 436.673,1720.96 "/>
<path clip-path="url(#clip322)" d="M436.954 1720.96 L436.954 1720.96 L437.236 1720.96 L437.236 1720.96 L436.954 1720.96 L436.954 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="436.954,1720.96 436.954,1720.96 437.236,1720.96 436.954,1720.96 "/>
<path clip-path="url(#clip322)" d="M437.236 1720.96 L437.236 1720.96 L437.518 1720.96 L437.518 1720.96 L437.236 1720.96 L437.236 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="437.236,1720.96 437.236,1720.96 437.518,1720.96 437.236,1720.96 "/>
<path clip-path="url(#clip322)" d="M437.518 1720.96 L437.518 1720.96 L437.799 1720.96 L437.799 1720.96 L437.518 1720.96 L437.518 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="437.518,1720.96 437.518,1720.96 437.799,1720.96 437.518,1720.96 "/>
<path clip-path="url(#clip322)" d="M437.799 1720.96 L437.799 1720.96 L438.081 1720.96 L438.081 1720.96 L437.799 1720.96 L437.799 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="437.799,1720.96 437.799,1720.96 438.081,1720.96 437.799,1720.96 "/>
<path clip-path="url(#clip322)" d="M438.081 1720.96 L438.081 1720.96 L438.363 1720.96 L438.363 1720.96 L438.081 1720.96 L438.081 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="438.081,1720.96 438.081,1720.96 438.363,1720.96 438.081,1720.96 "/>
<path clip-path="url(#clip322)" d="M438.363 1720.96 L438.363 1720.96 L438.645 1720.96 L438.645 1720.96 L438.363 1720.96 L438.363 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="438.363,1720.96 438.363,1720.96 438.645,1720.96 438.363,1720.96 "/>
<path clip-path="url(#clip322)" d="M438.645 1720.96 L438.645 1720.96 L438.926 1720.96 L438.926 1720.96 L438.645 1720.96 L438.645 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="438.645,1720.96 438.645,1720.96 438.926,1720.96 438.645,1720.96 "/>
<path clip-path="url(#clip322)" d="M438.926 1720.96 L438.926 1720.96 L439.208 1720.96 L439.208 1720.96 L438.926 1720.96 L438.926 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="438.926,1720.96 438.926,1720.96 439.208,1720.96 438.926,1720.96 "/>
<path clip-path="url(#clip322)" d="M439.208 1720.96 L439.208 1720.96 L439.49 1720.96 L439.49 1720.96 L439.208 1720.96 L439.208 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="439.208,1720.96 439.208,1720.96 439.49,1720.96 439.208,1720.96 "/>
<path clip-path="url(#clip322)" d="M439.49 1720.96 L439.49 1720.96 L439.771 1720.96 L439.771 1720.96 L439.49 1720.96 L439.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="439.49,1720.96 439.49,1720.96 439.771,1720.96 439.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M439.771 1720.96 L439.771 1720.96 L440.053 1720.96 L440.053 1720.96 L439.771 1720.96 L439.771 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="439.771,1720.96 439.771,1720.96 440.053,1720.96 439.771,1720.96 "/>
<path clip-path="url(#clip322)" d="M440.053 1720.96 L440.053 1720.96 L440.335 1720.96 L440.335 1720.96 L440.053 1720.96 L440.053 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="440.053,1720.96 440.053,1720.96 440.335,1720.96 440.053,1720.96 "/>
<path clip-path="url(#clip322)" d="M440.335 1720.96 L440.335 1720.96 L440.617 1720.96 L440.617 1720.96 L440.335 1720.96 L440.335 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="440.335,1720.96 440.335,1720.96 440.617,1720.96 440.335,1720.96 "/>
<path clip-path="url(#clip322)" d="M440.617 1720.96 L440.617 1720.96 L440.898 1720.96 L440.898 1720.96 L440.617 1720.96 L440.617 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="440.617,1720.96 440.617,1720.96 440.898,1720.96 440.617,1720.96 "/>
<path clip-path="url(#clip322)" d="M440.898 1720.96 L440.898 1720.96 L441.18 1720.96 L441.18 1720.96 L440.898 1720.96 L440.898 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="440.898,1720.96 440.898,1720.96 441.18,1720.96 440.898,1720.96 "/>
<path clip-path="url(#clip322)" d="M441.18 1720.96 L441.18 1720.96 L441.462 1720.96 L441.462 1720.96 L441.18 1720.96 L441.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="441.18,1720.96 441.18,1720.96 441.462,1720.96 441.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M441.462 1720.96 L441.462 1720.96 L441.744 1720.96 L441.744 1720.96 L441.462 1720.96 L441.462 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="441.462,1720.96 441.462,1720.96 441.744,1720.96 441.462,1720.96 "/>
<path clip-path="url(#clip322)" d="M441.744 1720.96 L441.744 1720.96 L442.025 1720.96 L442.025 1720.96 L441.744 1720.96 L441.744 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="441.744,1720.96 441.744,1720.96 442.025,1720.96 441.744,1720.96 "/>
<path clip-path="url(#clip322)" d="M442.025 1720.96 L442.025 1720.96 L442.307 1720.96 L442.307 1720.96 L442.025 1720.96 L442.025 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="442.025,1720.96 442.025,1720.96 442.307,1720.96 442.025,1720.96 "/>
<path clip-path="url(#clip322)" d="M442.307 1720.96 L442.307 1720.96 L442.589 1720.96 L442.589 1720.96 L442.307 1720.96 L442.307 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="442.307,1720.96 442.307,1720.96 442.589,1720.96 442.307,1720.96 "/>
<path clip-path="url(#clip322)" d="M442.589 1720.96 L442.589 1720.96 L442.87 1720.96 L442.87 1720.96 L442.589 1720.96 L442.589 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="442.589,1720.96 442.589,1720.96 442.87,1720.96 442.589,1720.96 "/>
<path clip-path="url(#clip322)" d="M442.87 1720.96 L442.87 1720.96 L443.152 1720.96 L443.152 1720.96 L442.87 1720.96 L442.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="442.87,1720.96 442.87,1720.96 443.152,1720.96 442.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M443.152 1720.96 L443.152 1720.96 L443.434 1720.96 L443.434 1720.96 L443.152 1720.96 L443.152 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="443.152,1720.96 443.152,1720.96 443.434,1720.96 443.152,1720.96 "/>
<path clip-path="url(#clip322)" d="M443.434 1720.96 L443.434 1720.96 L443.716 1720.96 L443.716 1720.96 L443.434 1720.96 L443.434 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="443.434,1720.96 443.434,1720.96 443.716,1720.96 443.434,1720.96 "/>
<path clip-path="url(#clip322)" d="M443.716 1720.96 L443.716 1720.96 L443.997 1720.96 L443.997 1720.96 L443.716 1720.96 L443.716 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="443.716,1720.96 443.716,1720.96 443.997,1720.96 443.716,1720.96 "/>
<path clip-path="url(#clip322)" d="M443.997 1720.96 L443.997 1720.96 L444.279 1720.96 L444.279 1720.96 L443.997 1720.96 L443.997 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="443.997,1720.96 443.997,1720.96 444.279,1720.96 443.997,1720.96 "/>
<path clip-path="url(#clip322)" d="M444.279 1720.96 L444.279 1720.96 L444.561 1720.96 L444.561 1720.96 L444.279 1720.96 L444.279 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="444.279,1720.96 444.279,1720.96 444.561,1720.96 444.279,1720.96 "/>
<path clip-path="url(#clip322)" d="M444.561 1720.96 L444.561 1720.96 L444.843 1720.96 L444.843 1720.96 L444.561 1720.96 L444.561 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="444.561,1720.96 444.561,1720.96 444.843,1720.96 444.561,1720.96 "/>
<path clip-path="url(#clip322)" d="M444.843 1720.96 L444.843 1720.96 L445.124 1720.96 L445.124 1720.96 L444.843 1720.96 L444.843 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="444.843,1720.96 444.843,1720.96 445.124,1720.96 444.843,1720.96 "/>
<path clip-path="url(#clip322)" d="M445.124 1720.96 L445.124 1720.96 L445.406 1720.96 L445.406 1720.96 L445.124 1720.96 L445.124 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="445.124,1720.96 445.124,1720.96 445.406,1720.96 445.124,1720.96 "/>
<path clip-path="url(#clip322)" d="M445.406 1720.96 L445.406 1720.96 L445.688 1720.96 L445.688 1720.96 L445.406 1720.96 L445.406 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="445.406,1720.96 445.406,1720.96 445.688,1720.96 445.406,1720.96 "/>
<path clip-path="url(#clip322)" d="M445.688 1720.96 L445.688 1720.96 L445.969 1720.96 L445.969 1720.96 L445.688 1720.96 L445.688 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="445.688,1720.96 445.688,1720.96 445.969,1720.96 445.688,1720.96 "/>
<path clip-path="url(#clip322)" d="M445.969 1720.96 L445.969 1720.96 L446.251 1720.96 L446.251 1720.96 L445.969 1720.96 L445.969 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="445.969,1720.96 445.969,1720.96 446.251,1720.96 445.969,1720.96 "/>
<path clip-path="url(#clip322)" d="M446.251 1720.96 L446.251 1720.96 L446.533 1720.96 L446.533 1720.96 L446.251 1720.96 L446.251 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="446.251,1720.96 446.251,1720.96 446.533,1720.96 446.251,1720.96 "/>
<path clip-path="url(#clip322)" d="M446.533 1720.96 L446.533 1720.96 L446.815 1720.96 L446.815 1720.96 L446.533 1720.96 L446.533 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="446.533,1720.96 446.533,1720.96 446.815,1720.96 446.533,1720.96 "/>
<path clip-path="url(#clip322)" d="M446.815 1720.96 L446.815 1720.96 L447.096 1720.96 L447.096 1720.96 L446.815 1720.96 L446.815 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="446.815,1720.96 446.815,1720.96 447.096,1720.96 446.815,1720.96 "/>
<path clip-path="url(#clip322)" d="M447.096 1720.96 L447.096 1720.96 L447.378 1720.96 L447.378 1720.96 L447.096 1720.96 L447.096 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="447.096,1720.96 447.096,1720.96 447.378,1720.96 447.096,1720.96 "/>
<path clip-path="url(#clip322)" d="M447.378 1720.96 L447.378 1720.96 L447.66 1720.96 L447.66 1720.96 L447.378 1720.96 L447.378 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="447.378,1720.96 447.378,1720.96 447.66,1720.96 447.378,1720.96 "/>
<path clip-path="url(#clip322)" d="M447.66 1720.96 L447.66 1720.96 L447.942 1720.96 L447.942 1720.96 L447.66 1720.96 L447.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="447.66,1720.96 447.66,1720.96 447.942,1720.96 447.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M447.942 1720.96 L447.942 1720.96 L448.223 1720.96 L448.223 1720.96 L447.942 1720.96 L447.942 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="447.942,1720.96 447.942,1720.96 448.223,1720.96 447.942,1720.96 "/>
<path clip-path="url(#clip322)" d="M448.223 1720.96 L448.223 1720.96 L448.505 1720.96 L448.505 1720.96 L448.223 1720.96 L448.223 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="448.223,1720.96 448.223,1720.96 448.505,1720.96 448.223,1720.96 "/>
<path clip-path="url(#clip322)" d="M448.505 1720.96 L448.505 1720.96 L448.787 1720.96 L448.787 1720.96 L448.505 1720.96 L448.505 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="448.505,1720.96 448.505,1720.96 448.787,1720.96 448.505,1720.96 "/>
<path clip-path="url(#clip322)" d="M448.787 1720.96 L448.787 1720.96 L449.068 1720.96 L449.068 1720.96 L448.787 1720.96 L448.787 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="448.787,1720.96 448.787,1720.96 449.068,1720.96 448.787,1720.96 "/>
<path clip-path="url(#clip322)" d="M449.068 1720.96 L449.068 1720.96 L449.35 1720.96 L449.35 1720.96 L449.068 1720.96 L449.068 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="449.068,1720.96 449.068,1720.96 449.35,1720.96 449.068,1720.96 "/>
<path clip-path="url(#clip322)" d="M449.35 1720.96 L449.35 1720.96 L449.632 1720.96 L449.632 1720.96 L449.35 1720.96 L449.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="449.35,1720.96 449.35,1720.96 449.632,1720.96 449.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M449.632 1720.96 L449.632 1720.96 L449.914 1720.96 L449.914 1720.96 L449.632 1720.96 L449.632 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="449.632,1720.96 449.632,1720.96 449.914,1720.96 449.632,1720.96 "/>
<path clip-path="url(#clip322)" d="M449.914 1720.96 L449.914 1720.96 L450.195 1720.96 L450.195 1720.96 L449.914 1720.96 L449.914 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="449.914,1720.96 449.914,1720.96 450.195,1720.96 449.914,1720.96 "/>
<path clip-path="url(#clip322)" d="M450.195 1720.96 L450.195 1720.96 L450.477 1720.96 L450.477 1720.96 L450.195 1720.96 L450.195 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="450.195,1720.96 450.195,1720.96 450.477,1720.96 450.195,1720.96 "/>
<path clip-path="url(#clip322)" d="M450.477 1720.96 L450.477 1720.96 L450.759 1720.96 L450.759 1720.96 L450.477 1720.96 L450.477 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="450.477,1720.96 450.477,1720.96 450.759,1720.96 450.477,1720.96 "/>
<path clip-path="url(#clip322)" d="M450.759 1720.96 L450.759 1720.96 L451.041 1720.96 L451.041 1720.96 L450.759 1720.96 L450.759 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="450.759,1720.96 450.759,1720.96 451.041,1720.96 450.759,1720.96 "/>
<path clip-path="url(#clip322)" d="M451.041 1720.96 L451.041 1720.96 L451.322 1720.96 L451.322 1720.96 L451.041 1720.96 L451.041 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="451.041,1720.96 451.041,1720.96 451.322,1720.96 451.041,1720.96 "/>
<path clip-path="url(#clip322)" d="M451.322 1720.96 L451.322 1720.96 L451.604 1720.96 L451.604 1720.96 L451.322 1720.96 L451.322 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="451.322,1720.96 451.322,1720.96 451.604,1720.96 451.322,1720.96 "/>
<path clip-path="url(#clip322)" d="M451.604 1720.96 L451.604 1720.96 L451.886 1720.96 L451.886 1720.96 L451.604 1720.96 L451.604 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="451.604,1720.96 451.604,1720.96 451.886,1720.96 451.604,1720.96 "/>
<path clip-path="url(#clip322)" d="M451.886 1720.96 L451.886 1720.96 L452.167 1720.96 L452.167 1720.96 L451.886 1720.96 L451.886 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="451.886,1720.96 451.886,1720.96 452.167,1720.96 451.886,1720.96 "/>
<path clip-path="url(#clip322)" d="M452.167 1720.96 L452.167 1720.96 L452.449 1720.96 L452.449 1720.96 L452.167 1720.96 L452.167 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="452.167,1720.96 452.167,1720.96 452.449,1720.96 452.167,1720.96 "/>
<path clip-path="url(#clip322)" d="M452.449 1720.96 L452.449 1720.96 L452.731 1720.96 L452.731 1720.96 L452.449 1720.96 L452.449 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="452.449,1720.96 452.449,1720.96 452.731,1720.96 452.449,1720.96 "/>
<path clip-path="url(#clip322)" d="M452.731 1720.96 L452.731 1720.96 L453.013 1720.96 L453.013 1720.96 L452.731 1720.96 L452.731 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="452.731,1720.96 452.731,1720.96 453.013,1720.96 452.731,1720.96 "/>
<path clip-path="url(#clip322)" d="M453.013 1720.96 L453.013 1720.96 L453.294 1720.96 L453.294 1720.96 L453.013 1720.96 L453.013 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="453.013,1720.96 453.013,1720.96 453.294,1720.96 453.013,1720.96 "/>
<path clip-path="url(#clip322)" d="M453.294 1720.96 L453.294 1720.96 L453.576 1720.96 L453.576 1720.96 L453.294 1720.96 L453.294 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="453.294,1720.96 453.294,1720.96 453.576,1720.96 453.294,1720.96 "/>
<path clip-path="url(#clip322)" d="M453.576 1720.96 L453.576 1720.96 L453.858 1720.96 L453.858 1720.96 L453.576 1720.96 L453.576 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="453.576,1720.96 453.576,1720.96 453.858,1720.96 453.576,1720.96 "/>
<path clip-path="url(#clip322)" d="M453.858 1720.96 L453.858 1720.96 L454.139 1720.96 L454.139 1720.96 L453.858 1720.96 L453.858 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="453.858,1720.96 453.858,1720.96 454.139,1720.96 453.858,1720.96 "/>
<path clip-path="url(#clip322)" d="M454.139 1720.96 L454.139 1720.96 L454.421 1720.96 L454.421 1720.96 L454.139 1720.96 L454.139 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="454.139,1720.96 454.139,1720.96 454.421,1720.96 454.139,1720.96 "/>
<path clip-path="url(#clip322)" d="M454.421 1720.96 L454.421 1720.96 L454.703 1720.96 L454.703 1720.96 L454.421 1720.96 L454.421 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="454.421,1720.96 454.421,1720.96 454.703,1720.96 454.421,1720.96 "/>
<path clip-path="url(#clip322)" d="M454.703 1720.96 L454.703 1720.96 L454.985 1720.96 L454.985 1720.96 L454.703 1720.96 L454.703 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="454.703,1720.96 454.703,1720.96 454.985,1720.96 454.703,1720.96 "/>
<path clip-path="url(#clip322)" d="M454.985 1720.96 L454.985 1720.96 L455.266 1720.96 L455.266 1720.96 L454.985 1720.96 L454.985 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="454.985,1720.96 454.985,1720.96 455.266,1720.96 454.985,1720.96 "/>
<path clip-path="url(#clip322)" d="M455.266 1720.96 L455.266 1720.96 L455.548 1720.96 L455.548 1720.96 L455.266 1720.96 L455.266 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="455.266,1720.96 455.266,1720.96 455.548,1720.96 455.266,1720.96 "/>
<path clip-path="url(#clip322)" d="M455.548 1720.96 L455.548 1720.96 L455.83 1720.96 L455.83 1720.96 L455.548 1720.96 L455.548 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="455.548,1720.96 455.548,1720.96 455.83,1720.96 455.548,1720.96 "/>
<path clip-path="url(#clip322)" d="M455.83 1720.96 L455.83 1720.96 L456.112 1720.96 L456.112 1720.96 L455.83 1720.96 L455.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="455.83,1720.96 455.83,1720.96 456.112,1720.96 455.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M456.112 1720.96 L456.112 1720.96 L456.393 1720.96 L456.393 1720.96 L456.112 1720.96 L456.112 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="456.112,1720.96 456.112,1720.96 456.393,1720.96 456.112,1720.96 "/>
<path clip-path="url(#clip322)" d="M456.393 1720.96 L456.393 1720.96 L456.675 1720.96 L456.675 1720.96 L456.393 1720.96 L456.393 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="456.393,1720.96 456.393,1720.96 456.675,1720.96 456.393,1720.96 "/>
<path clip-path="url(#clip322)" d="M456.675 1720.96 L456.675 1720.96 L456.957 1720.96 L456.957 1720.96 L456.675 1720.96 L456.675 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="456.675,1720.96 456.675,1720.96 456.957,1720.96 456.675,1720.96 "/>
<path clip-path="url(#clip322)" d="M456.957 1720.96 L456.957 1720.96 L457.238 1720.96 L457.238 1720.96 L456.957 1720.96 L456.957 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="456.957,1720.96 456.957,1720.96 457.238,1720.96 456.957,1720.96 "/>
<path clip-path="url(#clip322)" d="M457.238 1720.96 L457.238 1720.96 L457.52 1720.96 L457.52 1720.96 L457.238 1720.96 L457.238 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="457.238,1720.96 457.238,1720.96 457.52,1720.96 457.238,1720.96 "/>
<path clip-path="url(#clip322)" d="M457.52 1720.96 L457.52 1720.96 L457.802 1720.96 L457.802 1720.96 L457.52 1720.96 L457.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="457.52,1720.96 457.52,1720.96 457.802,1720.96 457.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M457.802 1720.96 L457.802 1720.96 L458.084 1720.96 L458.084 1720.96 L457.802 1720.96 L457.802 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="457.802,1720.96 457.802,1720.96 458.084,1720.96 457.802,1720.96 "/>
<path clip-path="url(#clip322)" d="M458.084 1720.96 L458.084 1720.96 L458.365 1720.96 L458.365 1720.96 L458.084 1720.96 L458.084 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="458.084,1720.96 458.084,1720.96 458.365,1720.96 458.084,1720.96 "/>
<path clip-path="url(#clip322)" d="M458.365 1720.96 L458.365 1720.96 L458.647 1720.96 L458.647 1720.96 L458.365 1720.96 L458.365 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="458.365,1720.96 458.365,1720.96 458.647,1720.96 458.365,1720.96 "/>
<path clip-path="url(#clip322)" d="M458.647 1720.96 L458.647 1720.96 L458.929 1720.96 L458.929 1720.96 L458.647 1720.96 L458.647 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="458.647,1720.96 458.647,1720.96 458.929,1720.96 458.647,1720.96 "/>
<path clip-path="url(#clip322)" d="M458.929 1720.96 L458.929 1720.96 L459.211 1720.96 L459.211 1720.96 L458.929 1720.96 L458.929 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="458.929,1720.96 458.929,1720.96 459.211,1720.96 458.929,1720.96 "/>
<path clip-path="url(#clip322)" d="M459.211 1720.96 L459.211 1720.96 L459.492 1720.96 L459.492 1720.96 L459.211 1720.96 L459.211 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="459.211,1720.96 459.211,1720.96 459.492,1720.96 459.211,1720.96 "/>
<path clip-path="url(#clip322)" d="M459.492 1720.96 L459.492 1720.96 L459.774 1720.96 L459.774 1720.96 L459.492 1720.96 L459.492 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="459.492,1720.96 459.492,1720.96 459.774,1720.96 459.492,1720.96 "/>
<path clip-path="url(#clip322)" d="M459.774 1720.96 L459.774 1720.96 L460.056 1720.96 L460.056 1720.96 L459.774 1720.96 L459.774 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="459.774,1720.96 459.774,1720.96 460.056,1720.96 459.774,1720.96 "/>
<path clip-path="url(#clip322)" d="M460.056 1720.96 L460.056 1720.96 L460.337 1720.96 L460.337 1720.96 L460.056 1720.96 L460.056 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="460.056,1720.96 460.056,1720.96 460.337,1720.96 460.056,1720.96 "/>
<path clip-path="url(#clip322)" d="M460.337 1720.96 L460.337 1720.96 L460.619 1720.96 L460.619 1720.96 L460.337 1720.96 L460.337 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="460.337,1720.96 460.337,1720.96 460.619,1720.96 460.337,1720.96 "/>
<path clip-path="url(#clip322)" d="M460.619 1720.96 L460.619 1720.96 L460.901 1720.96 L460.901 1720.96 L460.619 1720.96 L460.619 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="460.619,1720.96 460.619,1720.96 460.901,1720.96 460.619,1720.96 "/>
<path clip-path="url(#clip322)" d="M460.901 1720.96 L460.901 1720.96 L461.183 1720.96 L461.183 1720.96 L460.901 1720.96 L460.901 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="460.901,1720.96 460.901,1720.96 461.183,1720.96 460.901,1720.96 "/>
<path clip-path="url(#clip322)" d="M461.183 1720.96 L461.183 1720.96 L461.464 1720.96 L461.464 1720.96 L461.183 1720.96 L461.183 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="461.183,1720.96 461.183,1720.96 461.464,1720.96 461.183,1720.96 "/>
<path clip-path="url(#clip322)" d="M461.464 1720.96 L461.464 1720.96 L461.746 1720.96 L461.746 1720.96 L461.464 1720.96 L461.464 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="461.464,1720.96 461.464,1720.96 461.746,1720.96 461.464,1720.96 "/>
<path clip-path="url(#clip322)" d="M461.746 1720.96 L461.746 1720.96 L462.028 1720.96 L462.028 1720.96 L461.746 1720.96 L461.746 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="461.746,1720.96 461.746,1720.96 462.028,1720.96 461.746,1720.96 "/>
<path clip-path="url(#clip322)" d="M462.028 1720.96 L462.028 1720.96 L462.31 1720.96 L462.31 1720.96 L462.028 1720.96 L462.028 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="462.028,1720.96 462.028,1720.96 462.31,1720.96 462.028,1720.96 "/>
<path clip-path="url(#clip322)" d="M462.31 1720.96 L462.31 1720.96 L462.591 1720.96 L462.591 1720.96 L462.31 1720.96 L462.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="462.31,1720.96 462.31,1720.96 462.591,1720.96 462.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M462.591 1720.96 L462.591 1720.96 L462.873 1720.96 L462.873 1720.96 L462.591 1720.96 L462.591 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="462.591,1720.96 462.591,1720.96 462.873,1720.96 462.591,1720.96 "/>
<path clip-path="url(#clip322)" d="M462.873 1720.96 L462.873 1720.96 L463.155 1720.96 L463.155 1720.96 L462.873 1720.96 L462.873 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="462.873,1720.96 462.873,1720.96 463.155,1720.96 462.873,1720.96 "/>
<path clip-path="url(#clip322)" d="M463.155 1720.96 L463.155 1720.96 L463.436 1720.96 L463.436 1720.96 L463.155 1720.96 L463.155 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="463.155,1720.96 463.155,1720.96 463.436,1720.96 463.155,1720.96 "/>
<path clip-path="url(#clip322)" d="M463.436 1720.96 L463.436 1720.96 L463.718 1720.96 L463.718 1720.96 L463.436 1720.96 L463.436 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="463.436,1720.96 463.436,1720.96 463.718,1720.96 463.436,1720.96 "/>
<path clip-path="url(#clip322)" d="M463.718 1720.96 L463.718 1720.96 L464 1720.96 L464 1720.96 L463.718 1720.96 L463.718 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="463.718,1720.96 463.718,1720.96 464,1720.96 463.718,1720.96 "/>
<path clip-path="url(#clip322)" d="M464 1720.96 L464 1720.96 L464.282 1720.96 L464.282 1720.96 L464 1720.96 L464 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="464,1720.96 464,1720.96 464.282,1720.96 464,1720.96 "/>
<path clip-path="url(#clip322)" d="M464.282 1720.96 L464.282 1720.96 L464.563 1720.96 L464.563 1720.96 L464.282 1720.96 L464.282 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="464.282,1720.96 464.282,1720.96 464.563,1720.96 464.282,1720.96 "/>
<path clip-path="url(#clip322)" d="M464.563 1720.96 L464.563 1720.96 L464.845 1720.96 L464.845 1720.96 L464.563 1720.96 L464.563 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="464.563,1720.96 464.563,1720.96 464.845,1720.96 464.563,1720.96 "/>
<path clip-path="url(#clip322)" d="M464.845 1720.96 L464.845 1720.96 L465.127 1720.96 L465.127 1720.96 L464.845 1720.96 L464.845 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="464.845,1720.96 464.845,1720.96 465.127,1720.96 464.845,1720.96 "/>
<path clip-path="url(#clip322)" d="M465.127 1720.96 L465.127 1720.96 L465.409 1720.96 L465.409 1720.96 L465.127 1720.96 L465.127 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="465.127,1720.96 465.127,1720.96 465.409,1720.96 465.127,1720.96 "/>
<path clip-path="url(#clip322)" d="M465.409 1720.96 L465.409 1720.96 L465.69 1720.96 L465.69 1720.96 L465.409 1720.96 L465.409 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="465.409,1720.96 465.409,1720.96 465.69,1720.96 465.409,1720.96 "/>
<path clip-path="url(#clip322)" d="M465.69 1720.96 L465.69 1720.96 L465.972 1720.96 L465.972 1720.96 L465.69 1720.96 L465.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="465.69,1720.96 465.69,1720.96 465.972,1720.96 465.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M465.972 1720.96 L465.972 1720.96 L466.254 1720.96 L466.254 1720.96 L465.972 1720.96 L465.972 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="465.972,1720.96 465.972,1720.96 466.254,1720.96 465.972,1720.96 "/>
<path clip-path="url(#clip322)" d="M466.254 1720.96 L466.254 1720.96 L466.535 1720.96 L466.535 1720.96 L466.254 1720.96 L466.254 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="466.254,1720.96 466.254,1720.96 466.535,1720.96 466.254,1720.96 "/>
<path clip-path="url(#clip322)" d="M466.535 1720.96 L466.535 1720.96 L466.817 1720.96 L466.817 1720.96 L466.535 1720.96 L466.535 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="466.535,1720.96 466.535,1720.96 466.817,1720.96 466.535,1720.96 "/>
<path clip-path="url(#clip322)" d="M466.817 1720.96 L466.817 1720.96 L467.099 1720.96 L467.099 1720.96 L466.817 1720.96 L466.817 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="466.817,1720.96 466.817,1720.96 467.099,1720.96 466.817,1720.96 "/>
<path clip-path="url(#clip322)" d="M467.099 1720.96 L467.099 1720.96 L467.381 1720.96 L467.381 1720.96 L467.099 1720.96 L467.099 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="467.099,1720.96 467.099,1720.96 467.381,1720.96 467.099,1720.96 "/>
<path clip-path="url(#clip322)" d="M467.381 1720.96 L467.381 1720.96 L467.662 1720.96 L467.662 1720.96 L467.381 1720.96 L467.381 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="467.381,1720.96 467.381,1720.96 467.662,1720.96 467.381,1720.96 "/>
<path clip-path="url(#clip322)" d="M467.662 1720.96 L467.662 1720.96 L467.944 1720.96 L467.944 1720.96 L467.662 1720.96 L467.662 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="467.662,1720.96 467.662,1720.96 467.944,1720.96 467.662,1720.96 "/>
<path clip-path="url(#clip322)" d="M467.944 1720.96 L467.944 1720.96 L468.226 1720.96 L468.226 1720.96 L467.944 1720.96 L467.944 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="467.944,1720.96 467.944,1720.96 468.226,1720.96 467.944,1720.96 "/>
<path clip-path="url(#clip322)" d="M468.226 1720.96 L468.226 1720.96 L468.507 1720.96 L468.507 1720.96 L468.226 1720.96 L468.226 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="468.226,1720.96 468.226,1720.96 468.507,1720.96 468.226,1720.96 "/>
<path clip-path="url(#clip322)" d="M468.507 1720.96 L468.507 1720.96 L468.789 1720.96 L468.789 1720.96 L468.507 1720.96 L468.507 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="468.507,1720.96 468.507,1720.96 468.789,1720.96 468.507,1720.96 "/>
<path clip-path="url(#clip322)" d="M468.789 1720.96 L468.789 1720.96 L469.071 1720.96 L469.071 1720.96 L468.789 1720.96 L468.789 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="468.789,1720.96 468.789,1720.96 469.071,1720.96 468.789,1720.96 "/>
<path clip-path="url(#clip322)" d="M469.071 1720.96 L469.071 1720.96 L469.353 1720.96 L469.353 1720.96 L469.071 1720.96 L469.071 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="469.071,1720.96 469.071,1720.96 469.353,1720.96 469.071,1720.96 "/>
<path clip-path="url(#clip322)" d="M469.353 1720.96 L469.353 1720.96 L469.634 1720.96 L469.634 1720.96 L469.353 1720.96 L469.353 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="469.353,1720.96 469.353,1720.96 469.634,1720.96 469.353,1720.96 "/>
<path clip-path="url(#clip322)" d="M469.634 1720.96 L469.634 1720.96 L469.916 1720.96 L469.916 1720.96 L469.634 1720.96 L469.634 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="469.634,1720.96 469.634,1720.96 469.916,1720.96 469.634,1720.96 "/>
<path clip-path="url(#clip322)" d="M469.916 1720.96 L469.916 1720.96 L470.198 1720.96 L470.198 1720.96 L469.916 1720.96 L469.916 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="469.916,1720.96 469.916,1720.96 470.198,1720.96 469.916,1720.96 "/>
<path clip-path="url(#clip322)" d="M470.198 1720.96 L470.198 1720.96 L470.48 1720.96 L470.48 1720.96 L470.198 1720.96 L470.198 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="470.198,1720.96 470.198,1720.96 470.48,1720.96 470.198,1720.96 "/>
<path clip-path="url(#clip322)" d="M470.48 1720.96 L470.48 1720.96 L470.761 1720.96 L470.761 1720.96 L470.48 1720.96 L470.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="470.48,1720.96 470.48,1720.96 470.761,1720.96 470.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M470.761 1720.96 L470.761 1720.96 L471.043 1720.96 L471.043 1720.96 L470.761 1720.96 L470.761 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="470.761,1720.96 470.761,1720.96 471.043,1720.96 470.761,1720.96 "/>
<path clip-path="url(#clip322)" d="M471.043 1720.96 L471.043 1720.96 L471.325 1720.96 L471.325 1720.96 L471.043 1720.96 L471.043 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="471.043,1720.96 471.043,1720.96 471.325,1720.96 471.043,1720.96 "/>
<path clip-path="url(#clip322)" d="M471.325 1720.96 L471.325 1720.96 L471.606 1720.96 L471.606 1720.96 L471.325 1720.96 L471.325 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="471.325,1720.96 471.325,1720.96 471.606,1720.96 471.325,1720.96 "/>
<path clip-path="url(#clip322)" d="M471.606 1720.96 L471.606 1720.96 L471.888 1720.96 L471.888 1720.96 L471.606 1720.96 L471.606 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="471.606,1720.96 471.606,1720.96 471.888,1720.96 471.606,1720.96 "/>
<path clip-path="url(#clip322)" d="M471.888 1720.96 L471.888 1720.96 L472.17 1720.96 L472.17 1720.96 L471.888 1720.96 L471.888 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="471.888,1720.96 471.888,1720.96 472.17,1720.96 471.888,1720.96 "/>
<path clip-path="url(#clip322)" d="M472.17 1720.96 L472.17 1720.96 L472.452 1720.96 L472.452 1720.96 L472.17 1720.96 L472.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="472.17,1720.96 472.17,1720.96 472.452,1720.96 472.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M472.452 1720.96 L472.452 1720.96 L472.733 1720.96 L472.733 1720.96 L472.452 1720.96 L472.452 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="472.452,1720.96 472.452,1720.96 472.733,1720.96 472.452,1720.96 "/>
<path clip-path="url(#clip322)" d="M472.733 1720.96 L472.733 1720.96 L473.015 1720.96 L473.015 1720.96 L472.733 1720.96 L472.733 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="472.733,1720.96 472.733,1720.96 473.015,1720.96 472.733,1720.96 "/>
<path clip-path="url(#clip322)" d="M473.015 1720.96 L473.015 1720.96 L473.297 1720.96 L473.297 1720.96 L473.015 1720.96 L473.015 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="473.015,1720.96 473.015,1720.96 473.297,1720.96 473.015,1720.96 "/>
<path clip-path="url(#clip322)" d="M473.297 1720.96 L473.297 1720.96 L473.579 1720.96 L473.579 1720.96 L473.297 1720.96 L473.297 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="473.297,1720.96 473.297,1720.96 473.579,1720.96 473.297,1720.96 "/>
<path clip-path="url(#clip322)" d="M473.579 1720.96 L473.579 1720.96 L473.86 1720.96 L473.86 1720.96 L473.579 1720.96 L473.579 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="473.579,1720.96 473.579,1720.96 473.86,1720.96 473.579,1720.96 "/>
<path clip-path="url(#clip322)" d="M473.86 1720.96 L473.86 1720.96 L474.142 1720.96 L474.142 1720.96 L473.86 1720.96 L473.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="473.86,1720.96 473.86,1720.96 474.142,1720.96 473.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M474.142 1720.96 L474.142 1720.96 L474.424 1720.96 L474.424 1720.96 L474.142 1720.96 L474.142 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="474.142,1720.96 474.142,1720.96 474.424,1720.96 474.142,1720.96 "/>
<path clip-path="url(#clip322)" d="M474.424 1720.96 L474.424 1720.96 L474.705 1720.96 L474.705 1720.96 L474.424 1720.96 L474.424 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="474.424,1720.96 474.424,1720.96 474.705,1720.96 474.424,1720.96 "/>
<path clip-path="url(#clip322)" d="M474.705 1720.96 L474.705 1720.96 L474.987 1720.96 L474.987 1720.96 L474.705 1720.96 L474.705 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="474.705,1720.96 474.705,1720.96 474.987,1720.96 474.705,1720.96 "/>
<path clip-path="url(#clip322)" d="M474.987 1720.96 L474.987 1720.96 L475.269 1720.96 L475.269 1720.96 L474.987 1720.96 L474.987 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="474.987,1720.96 474.987,1720.96 475.269,1720.96 474.987,1720.96 "/>
<path clip-path="url(#clip322)" d="M475.269 1720.96 L475.269 1720.96 L475.551 1720.96 L475.551 1720.96 L475.269 1720.96 L475.269 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="475.269,1720.96 475.269,1720.96 475.551,1720.96 475.269,1720.96 "/>
<path clip-path="url(#clip322)" d="M475.551 1720.96 L475.551 1720.96 L475.832 1720.96 L475.832 1720.96 L475.551 1720.96 L475.551 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="475.551,1720.96 475.551,1720.96 475.832,1720.96 475.551,1720.96 "/>
<path clip-path="url(#clip322)" d="M475.832 1720.96 L475.832 1720.96 L476.114 1720.96 L476.114 1720.96 L475.832 1720.96 L475.832 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="475.832,1720.96 475.832,1720.96 476.114,1720.96 475.832,1720.96 "/>
<path clip-path="url(#clip322)" d="M476.114 1720.96 L476.114 1720.96 L476.396 1720.96 L476.396 1720.96 L476.114 1720.96 L476.114 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="476.114,1720.96 476.114,1720.96 476.396,1720.96 476.114,1720.96 "/>
<path clip-path="url(#clip322)" d="M476.396 1720.96 L476.396 1720.96 L476.678 1720.96 L476.678 1720.96 L476.396 1720.96 L476.396 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="476.396,1720.96 476.396,1720.96 476.678,1720.96 476.396,1720.96 "/>
<path clip-path="url(#clip322)" d="M476.678 1720.96 L476.678 1720.96 L476.959 1720.96 L476.959 1720.96 L476.678 1720.96 L476.678 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="476.678,1720.96 476.678,1720.96 476.959,1720.96 476.678,1720.96 "/>
<path clip-path="url(#clip322)" d="M476.959 1720.96 L476.959 1720.96 L477.241 1720.96 L477.241 1720.96 L476.959 1720.96 L476.959 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="476.959,1720.96 476.959,1720.96 477.241,1720.96 476.959,1720.96 "/>
<path clip-path="url(#clip322)" d="M477.241 1720.96 L477.241 1720.96 L477.523 1720.96 L477.523 1720.96 L477.241 1720.96 L477.241 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="477.241,1720.96 477.241,1720.96 477.523,1720.96 477.241,1720.96 "/>
<path clip-path="url(#clip322)" d="M477.523 1720.96 L477.523 1720.96 L477.804 1720.96 L477.804 1720.96 L477.523 1720.96 L477.523 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="477.523,1720.96 477.523,1720.96 477.804,1720.96 477.523,1720.96 "/>
<path clip-path="url(#clip322)" d="M477.804 1720.96 L477.804 1720.96 L478.086 1720.96 L478.086 1720.96 L477.804 1720.96 L477.804 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="477.804,1720.96 477.804,1720.96 478.086,1720.96 477.804,1720.96 "/>
<path clip-path="url(#clip322)" d="M478.086 1720.96 L478.086 1720.96 L478.368 1720.96 L478.368 1720.96 L478.086 1720.96 L478.086 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="478.086,1720.96 478.086,1720.96 478.368,1720.96 478.086,1720.96 "/>
<path clip-path="url(#clip322)" d="M478.368 1720.96 L478.368 1720.96 L478.65 1720.96 L478.65 1720.96 L478.368 1720.96 L478.368 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="478.368,1720.96 478.368,1720.96 478.65,1720.96 478.368,1720.96 "/>
<path clip-path="url(#clip322)" d="M478.65 1720.96 L478.65 1720.96 L478.931 1720.96 L478.931 1720.96 L478.65 1720.96 L478.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="478.65,1720.96 478.65,1720.96 478.931,1720.96 478.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M478.931 1720.96 L478.931 1720.96 L479.213 1720.96 L479.213 1720.96 L478.931 1720.96 L478.931 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="478.931,1720.96 478.931,1720.96 479.213,1720.96 478.931,1720.96 "/>
<path clip-path="url(#clip322)" d="M479.213 1720.96 L479.213 1720.96 L479.495 1720.96 L479.495 1720.96 L479.213 1720.96 L479.213 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="479.213,1720.96 479.213,1720.96 479.495,1720.96 479.213,1720.96 "/>
<path clip-path="url(#clip322)" d="M479.495 1720.96 L479.495 1720.96 L479.777 1720.96 L479.777 1720.96 L479.495 1720.96 L479.495 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="479.495,1720.96 479.495,1720.96 479.777,1720.96 479.495,1720.96 "/>
<path clip-path="url(#clip322)" d="M479.777 1720.96 L479.777 1720.96 L480.058 1720.96 L480.058 1720.96 L479.777 1720.96 L479.777 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="479.777,1720.96 479.777,1720.96 480.058,1720.96 479.777,1720.96 "/>
<path clip-path="url(#clip322)" d="M480.058 1720.96 L480.058 1720.96 L480.34 1720.96 L480.34 1720.96 L480.058 1720.96 L480.058 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="480.058,1720.96 480.058,1720.96 480.34,1720.96 480.058,1720.96 "/>
<path clip-path="url(#clip322)" d="M480.34 1720.96 L480.34 1720.96 L480.622 1720.96 L480.622 1720.96 L480.34 1720.96 L480.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="480.34,1720.96 480.34,1720.96 480.622,1720.96 480.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M480.622 1720.96 L480.622 1720.96 L480.903 1720.96 L480.903 1720.96 L480.622 1720.96 L480.622 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="480.622,1720.96 480.622,1720.96 480.903,1720.96 480.622,1720.96 "/>
<path clip-path="url(#clip322)" d="M480.903 1720.96 L480.903 1720.96 L481.185 1720.96 L481.185 1720.96 L480.903 1720.96 L480.903 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="480.903,1720.96 480.903,1720.96 481.185,1720.96 480.903,1720.96 "/>
<path clip-path="url(#clip322)" d="M481.185 1720.96 L481.185 1720.96 L481.467 1720.96 L481.467 1720.96 L481.185 1720.96 L481.185 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="481.185,1720.96 481.185,1720.96 481.467,1720.96 481.185,1720.96 "/>
<path clip-path="url(#clip322)" d="M481.467 1720.96 L481.467 1720.96 L481.749 1720.96 L481.749 1720.96 L481.467 1720.96 L481.467 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="481.467,1720.96 481.467,1720.96 481.749,1720.96 481.467,1720.96 "/>
<path clip-path="url(#clip322)" d="M481.749 1720.96 L481.749 1720.96 L482.03 1720.96 L482.03 1720.96 L481.749 1720.96 L481.749 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="481.749,1720.96 481.749,1720.96 482.03,1720.96 481.749,1720.96 "/>
<path clip-path="url(#clip322)" d="M482.03 1720.96 L482.03 1720.96 L482.312 1720.96 L482.312 1720.96 L482.03 1720.96 L482.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="482.03,1720.96 482.03,1720.96 482.312,1720.96 482.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M482.312 1720.96 L482.312 1720.96 L482.594 1720.96 L482.594 1720.96 L482.312 1720.96 L482.312 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="482.312,1720.96 482.312,1720.96 482.594,1720.96 482.312,1720.96 "/>
<path clip-path="url(#clip322)" d="M482.594 1720.96 L482.594 1720.96 L482.876 1720.96 L482.876 1720.96 L482.594 1720.96 L482.594 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="482.594,1720.96 482.594,1720.96 482.876,1720.96 482.594,1720.96 "/>
<path clip-path="url(#clip322)" d="M482.876 1720.96 L482.876 1720.96 L483.157 1720.96 L483.157 1720.96 L482.876 1720.96 L482.876 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="482.876,1720.96 482.876,1720.96 483.157,1720.96 482.876,1720.96 "/>
<path clip-path="url(#clip322)" d="M483.157 1720.96 L483.157 1720.96 L483.439 1720.96 L483.439 1720.96 L483.157 1720.96 L483.157 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="483.157,1720.96 483.157,1720.96 483.439,1720.96 483.157,1720.96 "/>
<path clip-path="url(#clip322)" d="M483.439 1720.96 L483.439 1720.96 L483.721 1720.96 L483.721 1720.96 L483.439 1720.96 L483.439 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="483.439,1720.96 483.439,1720.96 483.721,1720.96 483.439,1720.96 "/>
<path clip-path="url(#clip322)" d="M483.721 1720.96 L483.721 1720.96 L484.002 1720.96 L484.002 1720.96 L483.721 1720.96 L483.721 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="483.721,1720.96 483.721,1720.96 484.002,1720.96 483.721,1720.96 "/>
<path clip-path="url(#clip322)" d="M484.002 1720.96 L484.002 1720.96 L484.284 1720.96 L484.284 1720.96 L484.002 1720.96 L484.002 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="484.002,1720.96 484.002,1720.96 484.284,1720.96 484.002,1720.96 "/>
<path clip-path="url(#clip322)" d="M484.284 1720.96 L484.284 1720.96 L484.566 1720.96 L484.566 1720.96 L484.284 1720.96 L484.284 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="484.284,1720.96 484.284,1720.96 484.566,1720.96 484.284,1720.96 "/>
<path clip-path="url(#clip322)" d="M484.566 1720.96 L484.566 1720.96 L484.848 1720.96 L484.848 1720.96 L484.566 1720.96 L484.566 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="484.566,1720.96 484.566,1720.96 484.848,1720.96 484.566,1720.96 "/>
<path clip-path="url(#clip322)" d="M484.848 1720.96 L484.848 1720.96 L485.129 1720.96 L485.129 1720.96 L484.848 1720.96 L484.848 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="484.848,1720.96 484.848,1720.96 485.129,1720.96 484.848,1720.96 "/>
<path clip-path="url(#clip322)" d="M485.129 1720.96 L485.129 1720.96 L485.411 1720.96 L485.411 1720.96 L485.129 1720.96 L485.129 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="485.129,1720.96 485.129,1720.96 485.411,1720.96 485.129,1720.96 "/>
<path clip-path="url(#clip322)" d="M485.411 1720.96 L485.411 1720.96 L485.693 1720.96 L485.693 1720.96 L485.411 1720.96 L485.411 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="485.411,1720.96 485.411,1720.96 485.693,1720.96 485.411,1720.96 "/>
<path clip-path="url(#clip322)" d="M485.693 1720.96 L485.693 1720.96 L485.974 1720.96 L485.974 1720.96 L485.693 1720.96 L485.693 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="485.693,1720.96 485.693,1720.96 485.974,1720.96 485.693,1720.96 "/>
<path clip-path="url(#clip322)" d="M485.974 1720.96 L485.974 1720.96 L486.256 1720.96 L486.256 1720.96 L485.974 1720.96 L485.974 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="485.974,1720.96 485.974,1720.96 486.256,1720.96 485.974,1720.96 "/>
<path clip-path="url(#clip322)" d="M486.256 1720.96 L486.256 1720.96 L486.538 1720.96 L486.538 1720.96 L486.256 1720.96 L486.256 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="486.256,1720.96 486.256,1720.96 486.538,1720.96 486.256,1720.96 "/>
<path clip-path="url(#clip322)" d="M486.538 1720.96 L486.538 1720.96 L486.82 1720.96 L486.82 1720.96 L486.538 1720.96 L486.538 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="486.538,1720.96 486.538,1720.96 486.82,1720.96 486.538,1720.96 "/>
<path clip-path="url(#clip322)" d="M486.82 1720.96 L486.82 1720.96 L487.101 1720.96 L487.101 1720.96 L486.82 1720.96 L486.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="486.82,1720.96 486.82,1720.96 487.101,1720.96 486.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M487.101 1720.96 L487.101 1720.96 L487.383 1720.96 L487.383 1720.96 L487.101 1720.96 L487.101 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="487.101,1720.96 487.101,1720.96 487.383,1720.96 487.101,1720.96 "/>
<path clip-path="url(#clip322)" d="M487.383 1720.96 L487.383 1720.96 L487.665 1720.96 L487.665 1720.96 L487.383 1720.96 L487.383 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="487.383,1720.96 487.383,1720.96 487.665,1720.96 487.383,1720.96 "/>
<path clip-path="url(#clip322)" d="M487.665 1720.96 L487.665 1720.96 L487.947 1720.96 L487.947 1720.96 L487.665 1720.96 L487.665 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="487.665,1720.96 487.665,1720.96 487.947,1720.96 487.665,1720.96 "/>
<path clip-path="url(#clip322)" d="M487.947 1720.96 L487.947 1720.96 L488.228 1720.96 L488.228 1720.96 L487.947 1720.96 L487.947 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="487.947,1720.96 487.947,1720.96 488.228,1720.96 487.947,1720.96 "/>
<path clip-path="url(#clip322)" d="M488.228 1720.96 L488.228 1720.96 L488.51 1720.96 L488.51 1720.96 L488.228 1720.96 L488.228 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="488.228,1720.96 488.228,1720.96 488.51,1720.96 488.228,1720.96 "/>
<path clip-path="url(#clip322)" d="M488.51 1720.96 L488.51 1720.96 L488.792 1720.96 L488.792 1720.96 L488.51 1720.96 L488.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="488.51,1720.96 488.51,1720.96 488.792,1720.96 488.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M488.792 1720.96 L488.792 1720.96 L489.073 1720.96 L489.073 1720.96 L488.792 1720.96 L488.792 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="488.792,1720.96 488.792,1720.96 489.073,1720.96 488.792,1720.96 "/>
<path clip-path="url(#clip322)" d="M489.073 1720.96 L489.073 1720.96 L489.355 1720.96 L489.355 1720.96 L489.073 1720.96 L489.073 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="489.073,1720.96 489.073,1720.96 489.355,1720.96 489.073,1720.96 "/>
<path clip-path="url(#clip322)" d="M489.355 1720.96 L489.355 1720.96 L489.637 1720.96 L489.637 1720.96 L489.355 1720.96 L489.355 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="489.355,1720.96 489.355,1720.96 489.637,1720.96 489.355,1720.96 "/>
<path clip-path="url(#clip322)" d="M489.637 1720.96 L489.637 1720.96 L489.919 1720.96 L489.919 1720.96 L489.637 1720.96 L489.637 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="489.637,1720.96 489.637,1720.96 489.919,1720.96 489.637,1720.96 "/>
<path clip-path="url(#clip322)" d="M489.919 1720.96 L489.919 1720.96 L490.2 1720.96 L490.2 1720.96 L489.919 1720.96 L489.919 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="489.919,1720.96 489.919,1720.96 490.2,1720.96 489.919,1720.96 "/>
<path clip-path="url(#clip322)" d="M490.2 1720.96 L490.2 1720.96 L490.482 1720.96 L490.482 1720.96 L490.2 1720.96 L490.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="490.2,1720.96 490.2,1720.96 490.482,1720.96 490.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M490.482 1720.96 L490.482 1720.96 L490.764 1720.96 L490.764 1720.96 L490.482 1720.96 L490.482 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="490.482,1720.96 490.482,1720.96 490.764,1720.96 490.482,1720.96 "/>
<path clip-path="url(#clip322)" d="M490.764 1720.96 L490.764 1720.96 L491.046 1720.96 L491.046 1720.96 L490.764 1720.96 L490.764 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="490.764,1720.96 490.764,1720.96 491.046,1720.96 490.764,1720.96 "/>
<path clip-path="url(#clip322)" d="M491.046 1720.96 L491.046 1720.96 L491.327 1720.96 L491.327 1720.96 L491.046 1720.96 L491.046 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="491.046,1720.96 491.046,1720.96 491.327,1720.96 491.046,1720.96 "/>
<path clip-path="url(#clip322)" d="M491.327 1720.96 L491.327 1720.96 L491.609 1720.96 L491.609 1720.96 L491.327 1720.96 L491.327 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="491.327,1720.96 491.327,1720.96 491.609,1720.96 491.327,1720.96 "/>
<path clip-path="url(#clip322)" d="M491.609 1720.96 L491.609 1720.96 L491.891 1720.96 L491.891 1720.96 L491.609 1720.96 L491.609 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="491.609,1720.96 491.609,1720.96 491.891,1720.96 491.609,1720.96 "/>
<path clip-path="url(#clip322)" d="M491.891 1720.96 L491.891 1720.96 L492.172 1720.96 L492.172 1720.96 L491.891 1720.96 L491.891 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="491.891,1720.96 491.891,1720.96 492.172,1720.96 491.891,1720.96 "/>
<path clip-path="url(#clip322)" d="M492.172 1720.96 L492.172 1720.96 L492.454 1720.96 L492.454 1720.96 L492.172 1720.96 L492.172 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="492.172,1720.96 492.172,1720.96 492.454,1720.96 492.172,1720.96 "/>
<path clip-path="url(#clip322)" d="M492.454 1720.96 L492.454 1720.96 L492.736 1720.96 L492.736 1720.96 L492.454 1720.96 L492.454 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="492.454,1720.96 492.454,1720.96 492.736,1720.96 492.454,1720.96 "/>
<path clip-path="url(#clip322)" d="M492.736 1720.96 L492.736 1720.96 L493.018 1720.96 L493.018 1720.96 L492.736 1720.96 L492.736 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="492.736,1720.96 492.736,1720.96 493.018,1720.96 492.736,1720.96 "/>
<path clip-path="url(#clip322)" d="M493.018 1720.96 L493.018 1720.96 L493.299 1720.96 L493.299 1720.96 L493.018 1720.96 L493.018 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="493.018,1720.96 493.018,1720.96 493.299,1720.96 493.018,1720.96 "/>
<path clip-path="url(#clip322)" d="M493.299 1720.96 L493.299 1720.96 L493.581 1720.96 L493.581 1720.96 L493.299 1720.96 L493.299 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="493.299,1720.96 493.299,1720.96 493.581,1720.96 493.299,1720.96 "/>
<path clip-path="url(#clip322)" d="M493.581 1720.96 L493.581 1720.96 L493.863 1720.96 L493.863 1720.96 L493.581 1720.96 L493.581 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="493.581,1720.96 493.581,1720.96 493.863,1720.96 493.581,1720.96 "/>
<path clip-path="url(#clip322)" d="M493.863 1720.96 L493.863 1720.96 L494.145 1720.96 L494.145 1720.96 L493.863 1720.96 L493.863 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="493.863,1720.96 493.863,1720.96 494.145,1720.96 493.863,1720.96 "/>
<path clip-path="url(#clip322)" d="M494.145 1720.96 L494.145 1720.96 L494.426 1720.96 L494.426 1720.96 L494.145 1720.96 L494.145 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="494.145,1720.96 494.145,1720.96 494.426,1720.96 494.145,1720.96 "/>
<path clip-path="url(#clip322)" d="M494.426 1720.96 L494.426 1720.96 L494.708 1720.96 L494.708 1720.96 L494.426 1720.96 L494.426 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="494.426,1720.96 494.426,1720.96 494.708,1720.96 494.426,1720.96 "/>
<path clip-path="url(#clip322)" d="M494.708 1720.96 L494.708 1720.96 L494.99 1720.96 L494.99 1720.96 L494.708 1720.96 L494.708 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="494.708,1720.96 494.708,1720.96 494.99,1720.96 494.708,1720.96 "/>
<path clip-path="url(#clip322)" d="M494.99 1720.96 L494.99 1720.96 L495.271 1720.96 L495.271 1720.96 L494.99 1720.96 L494.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="494.99,1720.96 494.99,1720.96 495.271,1720.96 494.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M495.271 1720.96 L495.271 1720.96 L495.553 1720.96 L495.553 1720.96 L495.271 1720.96 L495.271 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="495.271,1720.96 495.271,1720.96 495.553,1720.96 495.271,1720.96 "/>
<path clip-path="url(#clip322)" d="M495.553 1720.96 L495.553 1720.96 L495.835 1720.96 L495.835 1720.96 L495.553 1720.96 L495.553 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="495.553,1720.96 495.553,1720.96 495.835,1720.96 495.553,1720.96 "/>
<path clip-path="url(#clip322)" d="M495.835 1720.96 L495.835 1720.96 L496.117 1720.96 L496.117 1720.96 L495.835 1720.96 L495.835 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="495.835,1720.96 495.835,1720.96 496.117,1720.96 495.835,1720.96 "/>
<path clip-path="url(#clip322)" d="M496.117 1720.96 L496.117 1720.96 L496.398 1720.96 L496.398 1720.96 L496.117 1720.96 L496.117 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="496.117,1720.96 496.117,1720.96 496.398,1720.96 496.117,1720.96 "/>
<path clip-path="url(#clip322)" d="M496.398 1720.96 L496.398 1720.96 L496.68 1720.96 L496.68 1720.96 L496.398 1720.96 L496.398 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="496.398,1720.96 496.398,1720.96 496.68,1720.96 496.398,1720.96 "/>
<path clip-path="url(#clip322)" d="M496.68 1720.96 L496.68 1720.96 L496.962 1720.96 L496.962 1720.96 L496.68 1720.96 L496.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="496.68,1720.96 496.68,1720.96 496.962,1720.96 496.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M496.962 1720.96 L496.962 1720.96 L497.244 1720.96 L497.244 1720.96 L496.962 1720.96 L496.962 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="496.962,1720.96 496.962,1720.96 497.244,1720.96 496.962,1720.96 "/>
<path clip-path="url(#clip322)" d="M497.244 1720.96 L497.244 1720.96 L497.525 1720.96 L497.525 1720.96 L497.244 1720.96 L497.244 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="497.244,1720.96 497.244,1720.96 497.525,1720.96 497.244,1720.96 "/>
<path clip-path="url(#clip322)" d="M497.525 1720.96 L497.525 1720.96 L497.807 1720.96 L497.807 1720.96 L497.525 1720.96 L497.525 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="497.525,1720.96 497.525,1720.96 497.807,1720.96 497.525,1720.96 "/>
<path clip-path="url(#clip322)" d="M497.807 1720.96 L497.807 1720.96 L498.089 1720.96 L498.089 1720.96 L497.807 1720.96 L497.807 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="497.807,1720.96 497.807,1720.96 498.089,1720.96 497.807,1720.96 "/>
<path clip-path="url(#clip322)" d="M498.089 1720.96 L498.089 1720.96 L498.37 1720.96 L498.37 1720.96 L498.089 1720.96 L498.089 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="498.089,1720.96 498.089,1720.96 498.37,1720.96 498.089,1720.96 "/>
<path clip-path="url(#clip322)" d="M498.37 1720.96 L498.37 1720.96 L498.652 1720.96 L498.652 1720.96 L498.37 1720.96 L498.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="498.37,1720.96 498.37,1720.96 498.652,1720.96 498.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M498.652 1720.96 L498.652 1720.96 L498.934 1720.96 L498.934 1720.96 L498.652 1720.96 L498.652 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="498.652,1720.96 498.652,1720.96 498.934,1720.96 498.652,1720.96 "/>
<path clip-path="url(#clip322)" d="M498.934 1720.96 L498.934 1720.96 L499.216 1720.96 L499.216 1720.96 L498.934 1720.96 L498.934 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="498.934,1720.96 498.934,1720.96 499.216,1720.96 498.934,1720.96 "/>
<path clip-path="url(#clip322)" d="M499.216 1720.96 L499.216 1720.96 L499.497 1720.96 L499.497 1720.96 L499.216 1720.96 L499.216 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="499.216,1720.96 499.216,1720.96 499.497,1720.96 499.216,1720.96 "/>
<path clip-path="url(#clip322)" d="M499.497 1720.96 L499.497 1720.96 L499.779 1720.96 L499.779 1720.96 L499.497 1720.96 L499.497 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="499.497,1720.96 499.497,1720.96 499.779,1720.96 499.497,1720.96 "/>
<path clip-path="url(#clip322)" d="M499.779 1720.96 L499.779 1720.96 L500.061 1720.96 L500.061 1720.96 L499.779 1720.96 L499.779 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="499.779,1720.96 499.779,1720.96 500.061,1720.96 499.779,1720.96 "/>
<path clip-path="url(#clip322)" d="M500.061 1720.96 L500.061 1720.96 L500.342 1720.96 L500.342 1720.96 L500.061 1720.96 L500.061 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="500.061,1720.96 500.061,1720.96 500.342,1720.96 500.061,1720.96 "/>
<path clip-path="url(#clip322)" d="M500.342 1720.96 L500.342 1720.96 L500.624 1720.96 L500.624 1720.96 L500.342 1720.96 L500.342 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="500.342,1720.96 500.342,1720.96 500.624,1720.96 500.342,1720.96 "/>
<path clip-path="url(#clip322)" d="M500.624 1720.96 L500.624 1720.96 L500.906 1720.96 L500.906 1720.96 L500.624 1720.96 L500.624 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="500.624,1720.96 500.624,1720.96 500.906,1720.96 500.624,1720.96 "/>
<path clip-path="url(#clip322)" d="M500.906 1720.96 L500.906 1720.96 L501.188 1720.96 L501.188 1720.96 L500.906 1720.96 L500.906 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="500.906,1720.96 500.906,1720.96 501.188,1720.96 500.906,1720.96 "/>
<path clip-path="url(#clip322)" d="M501.188 1720.96 L501.188 1720.96 L501.469 1720.96 L501.469 1720.96 L501.188 1720.96 L501.188 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="501.188,1720.96 501.188,1720.96 501.469,1720.96 501.188,1720.96 "/>
<path clip-path="url(#clip322)" d="M501.469 1720.96 L501.469 1720.96 L501.751 1720.96 L501.751 1720.96 L501.469 1720.96 L501.469 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="501.469,1720.96 501.469,1720.96 501.751,1720.96 501.469,1720.96 "/>
<path clip-path="url(#clip322)" d="M501.751 1720.96 L501.751 1720.96 L502.033 1720.96 L502.033 1720.96 L501.751 1720.96 L501.751 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="501.751,1720.96 501.751,1720.96 502.033,1720.96 501.751,1720.96 "/>
<path clip-path="url(#clip322)" d="M502.033 1720.96 L502.033 1720.96 L502.315 1720.96 L502.315 1720.96 L502.033 1720.96 L502.033 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="502.033,1720.96 502.033,1720.96 502.315,1720.96 502.033,1720.96 "/>
<path clip-path="url(#clip322)" d="M502.315 1720.96 L502.315 1720.96 L502.596 1720.96 L502.596 1720.96 L502.315 1720.96 L502.315 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="502.315,1720.96 502.315,1720.96 502.596,1720.96 502.315,1720.96 "/>
<path clip-path="url(#clip322)" d="M502.596 1720.96 L502.596 1720.96 L502.878 1720.96 L502.878 1720.96 L502.596 1720.96 L502.596 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="502.596,1720.96 502.596,1720.96 502.878,1720.96 502.596,1720.96 "/>
<path clip-path="url(#clip322)" d="M502.878 1720.96 L502.878 1720.96 L503.16 1720.96 L503.16 1720.96 L502.878 1720.96 L502.878 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="502.878,1720.96 502.878,1720.96 503.16,1720.96 502.878,1720.96 "/>
<path clip-path="url(#clip322)" d="M503.16 1720.96 L503.16 1720.96 L503.441 1720.96 L503.441 1720.96 L503.16 1720.96 L503.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="503.16,1720.96 503.16,1720.96 503.441,1720.96 503.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M503.441 1720.96 L503.441 1720.96 L503.723 1720.96 L503.723 1720.96 L503.441 1720.96 L503.441 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="503.441,1720.96 503.441,1720.96 503.723,1720.96 503.441,1720.96 "/>
<path clip-path="url(#clip322)" d="M503.723 1720.96 L503.723 1720.96 L504.005 1720.96 L504.005 1720.96 L503.723 1720.96 L503.723 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="503.723,1720.96 503.723,1720.96 504.005,1720.96 503.723,1720.96 "/>
<path clip-path="url(#clip322)" d="M504.005 1720.96 L504.005 1720.96 L504.287 1720.96 L504.287 1720.96 L504.005 1720.96 L504.005 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="504.005,1720.96 504.005,1720.96 504.287,1720.96 504.005,1720.96 "/>
<path clip-path="url(#clip322)" d="M504.287 1720.96 L504.287 1720.96 L504.568 1720.96 L504.568 1720.96 L504.287 1720.96 L504.287 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="504.287,1720.96 504.287,1720.96 504.568,1720.96 504.287,1720.96 "/>
<path clip-path="url(#clip322)" d="M504.568 1720.96 L504.568 1720.96 L504.85 1720.96 L504.85 1720.96 L504.568 1720.96 L504.568 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="504.568,1720.96 504.568,1720.96 504.85,1720.96 504.568,1720.96 "/>
<path clip-path="url(#clip322)" d="M504.85 1720.96 L504.85 1720.96 L505.132 1720.96 L505.132 1720.96 L504.85 1720.96 L504.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="504.85,1720.96 504.85,1720.96 505.132,1720.96 504.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M505.132 1720.96 L505.132 1720.96 L505.414 1720.96 L505.414 1720.96 L505.132 1720.96 L505.132 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="505.132,1720.96 505.132,1720.96 505.414,1720.96 505.132,1720.96 "/>
<path clip-path="url(#clip322)" d="M505.414 1720.96 L505.414 1720.96 L505.695 1720.96 L505.695 1720.96 L505.414 1720.96 L505.414 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="505.414,1720.96 505.414,1720.96 505.695,1720.96 505.414,1720.96 "/>
<path clip-path="url(#clip322)" d="M505.695 1720.96 L505.695 1720.96 L505.977 1720.96 L505.977 1720.96 L505.695 1720.96 L505.695 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="505.695,1720.96 505.695,1720.96 505.977,1720.96 505.695,1720.96 "/>
<path clip-path="url(#clip322)" d="M505.977 1720.96 L505.977 1720.96 L506.259 1720.96 L506.259 1720.96 L505.977 1720.96 L505.977 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="505.977,1720.96 505.977,1720.96 506.259,1720.96 505.977,1720.96 "/>
<path clip-path="url(#clip322)" d="M506.259 1720.96 L506.259 1720.96 L506.54 1720.96 L506.54 1720.96 L506.259 1720.96 L506.259 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="506.259,1720.96 506.259,1720.96 506.54,1720.96 506.259,1720.96 "/>
<path clip-path="url(#clip322)" d="M506.54 1720.96 L506.54 1720.96 L506.822 1720.96 L506.822 1720.96 L506.54 1720.96 L506.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="506.54,1720.96 506.54,1720.96 506.822,1720.96 506.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M506.822 1720.96 L506.822 1720.96 L507.104 1720.96 L507.104 1720.96 L506.822 1720.96 L506.822 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="506.822,1720.96 506.822,1720.96 507.104,1720.96 506.822,1720.96 "/>
<path clip-path="url(#clip322)" d="M507.104 1720.96 L507.104 1720.96 L507.386 1720.96 L507.386 1720.96 L507.104 1720.96 L507.104 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="507.104,1720.96 507.104,1720.96 507.386,1720.96 507.104,1720.96 "/>
<path clip-path="url(#clip322)" d="M507.386 1720.96 L507.386 1720.96 L507.667 1720.96 L507.667 1720.96 L507.386 1720.96 L507.386 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="507.386,1720.96 507.386,1720.96 507.667,1720.96 507.386,1720.96 "/>
<path clip-path="url(#clip322)" d="M507.667 1720.96 L507.667 1720.96 L507.949 1720.96 L507.949 1720.96 L507.667 1720.96 L507.667 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="507.667,1720.96 507.667,1720.96 507.949,1720.96 507.667,1720.96 "/>
<path clip-path="url(#clip322)" d="M507.949 1720.96 L507.949 1720.96 L508.231 1720.96 L508.231 1720.96 L507.949 1720.96 L507.949 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="507.949,1720.96 507.949,1720.96 508.231,1720.96 507.949,1720.96 "/>
<path clip-path="url(#clip322)" d="M508.231 1720.96 L508.231 1720.96 L508.513 1720.96 L508.513 1720.96 L508.231 1720.96 L508.231 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="508.231,1720.96 508.231,1720.96 508.513,1720.96 508.231,1720.96 "/>
<path clip-path="url(#clip322)" d="M508.513 1720.96 L508.513 1720.96 L508.794 1720.96 L508.794 1720.96 L508.513 1720.96 L508.513 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="508.513,1720.96 508.513,1720.96 508.794,1720.96 508.513,1720.96 "/>
<path clip-path="url(#clip322)" d="M508.794 1720.96 L508.794 1720.96 L509.076 1720.96 L509.076 1720.96 L508.794 1720.96 L508.794 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="508.794,1720.96 508.794,1720.96 509.076,1720.96 508.794,1720.96 "/>
<path clip-path="url(#clip322)" d="M509.076 1720.96 L509.076 1720.96 L509.358 1720.96 L509.358 1720.96 L509.076 1720.96 L509.076 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="509.076,1720.96 509.076,1720.96 509.358,1720.96 509.076,1720.96 "/>
<path clip-path="url(#clip322)" d="M509.358 1720.96 L509.358 1720.96 L509.639 1720.96 L509.639 1720.96 L509.358 1720.96 L509.358 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="509.358,1720.96 509.358,1720.96 509.639,1720.96 509.358,1720.96 "/>
<path clip-path="url(#clip322)" d="M509.639 1720.96 L509.639 1720.96 L509.921 1720.96 L509.921 1720.96 L509.639 1720.96 L509.639 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="509.639,1720.96 509.639,1720.96 509.921,1720.96 509.639,1720.96 "/>
<path clip-path="url(#clip322)" d="M509.921 1720.96 L509.921 1720.96 L510.203 1720.96 L510.203 1720.96 L509.921 1720.96 L509.921 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="509.921,1720.96 509.921,1720.96 510.203,1720.96 509.921,1720.96 "/>
<path clip-path="url(#clip322)" d="M510.203 1720.96 L510.203 1720.96 L510.485 1720.96 L510.485 1720.96 L510.203 1720.96 L510.203 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="510.203,1720.96 510.203,1720.96 510.485,1720.96 510.203,1720.96 "/>
<path clip-path="url(#clip322)" d="M510.485 1720.96 L510.485 1720.96 L510.766 1720.96 L510.766 1720.96 L510.485 1720.96 L510.485 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="510.485,1720.96 510.485,1720.96 510.766,1720.96 510.485,1720.96 "/>
<path clip-path="url(#clip322)" d="M510.766 1720.96 L510.766 1720.96 L511.048 1720.96 L511.048 1720.96 L510.766 1720.96 L510.766 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="510.766,1720.96 510.766,1720.96 511.048,1720.96 510.766,1720.96 "/>
<path clip-path="url(#clip322)" d="M511.048 1720.96 L511.048 1720.96 L511.33 1720.96 L511.33 1720.96 L511.048 1720.96 L511.048 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="511.048,1720.96 511.048,1720.96 511.33,1720.96 511.048,1720.96 "/>
<path clip-path="url(#clip322)" d="M511.33 1720.96 L511.33 1720.96 L511.612 1720.96 L511.612 1720.96 L511.33 1720.96 L511.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="511.33,1720.96 511.33,1720.96 511.612,1720.96 511.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M511.612 1720.96 L511.612 1720.96 L511.893 1720.96 L511.893 1720.96 L511.612 1720.96 L511.612 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="511.612,1720.96 511.612,1720.96 511.893,1720.96 511.612,1720.96 "/>
<path clip-path="url(#clip322)" d="M511.893 1720.96 L511.893 1720.96 L512.175 1720.96 L512.175 1720.96 L511.893 1720.96 L511.893 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="511.893,1720.96 511.893,1720.96 512.175,1720.96 511.893,1720.96 "/>
<path clip-path="url(#clip322)" d="M512.175 1720.96 L512.175 1720.96 L512.457 1720.96 L512.457 1720.96 L512.175 1720.96 L512.175 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="512.175,1720.96 512.175,1720.96 512.457,1720.96 512.175,1720.96 "/>
<path clip-path="url(#clip322)" d="M512.457 1720.96 L512.457 1720.96 L512.738 1720.96 L512.738 1720.96 L512.457 1720.96 L512.457 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="512.457,1720.96 512.457,1720.96 512.738,1720.96 512.457,1720.96 "/>
<path clip-path="url(#clip322)" d="M512.738 1720.96 L512.738 1720.96 L513.02 1720.96 L513.02 1720.96 L512.738 1720.96 L512.738 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="512.738,1720.96 512.738,1720.96 513.02,1720.96 512.738,1720.96 "/>
<path clip-path="url(#clip322)" d="M513.02 1720.96 L513.02 1720.96 L513.302 1720.96 L513.302 1720.96 L513.02 1720.96 L513.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="513.02,1720.96 513.02,1720.96 513.302,1720.96 513.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M513.302 1720.96 L513.302 1720.96 L513.584 1720.96 L513.584 1720.96 L513.302 1720.96 L513.302 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="513.302,1720.96 513.302,1720.96 513.584,1720.96 513.302,1720.96 "/>
<path clip-path="url(#clip322)" d="M513.584 1720.96 L513.584 1720.96 L513.865 1720.96 L513.865 1720.96 L513.584 1720.96 L513.584 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="513.584,1720.96 513.584,1720.96 513.865,1720.96 513.584,1720.96 "/>
<path clip-path="url(#clip322)" d="M513.865 1720.96 L513.865 1720.96 L514.147 1720.96 L514.147 1720.96 L513.865 1720.96 L513.865 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="513.865,1720.96 513.865,1720.96 514.147,1720.96 513.865,1720.96 "/>
<path clip-path="url(#clip322)" d="M514.147 1720.96 L514.147 1720.96 L514.429 1720.96 L514.429 1720.96 L514.147 1720.96 L514.147 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="514.147,1720.96 514.147,1720.96 514.429,1720.96 514.147,1720.96 "/>
<path clip-path="url(#clip322)" d="M514.429 1720.96 L514.429 1720.96 L514.71 1720.96 L514.71 1720.96 L514.429 1720.96 L514.429 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="514.429,1720.96 514.429,1720.96 514.71,1720.96 514.429,1720.96 "/>
<path clip-path="url(#clip322)" d="M514.71 1720.96 L514.71 1720.96 L514.992 1720.96 L514.992 1720.96 L514.71 1720.96 L514.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="514.71,1720.96 514.71,1720.96 514.992,1720.96 514.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M514.992 1720.96 L514.992 1720.96 L515.274 1720.96 L515.274 1720.96 L514.992 1720.96 L514.992 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="514.992,1720.96 514.992,1720.96 515.274,1720.96 514.992,1720.96 "/>
<path clip-path="url(#clip322)" d="M515.274 1720.96 L515.274 1720.96 L515.556 1720.96 L515.556 1720.96 L515.274 1720.96 L515.274 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="515.274,1720.96 515.274,1720.96 515.556,1720.96 515.274,1720.96 "/>
<path clip-path="url(#clip322)" d="M515.556 1720.96 L515.556 1720.96 L515.837 1720.96 L515.837 1720.96 L515.556 1720.96 L515.556 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="515.556,1720.96 515.556,1720.96 515.837,1720.96 515.556,1720.96 "/>
<path clip-path="url(#clip322)" d="M515.837 1720.96 L515.837 1720.96 L516.119 1720.96 L516.119 1720.96 L515.837 1720.96 L515.837 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="515.837,1720.96 515.837,1720.96 516.119,1720.96 515.837,1720.96 "/>
<path clip-path="url(#clip322)" d="M516.119 1720.96 L516.119 1720.96 L516.401 1720.96 L516.401 1720.96 L516.119 1720.96 L516.119 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="516.119,1720.96 516.119,1720.96 516.401,1720.96 516.119,1720.96 "/>
<path clip-path="url(#clip322)" d="M516.401 1720.96 L516.401 1720.96 L516.683 1720.96 L516.683 1720.96 L516.401 1720.96 L516.401 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="516.401,1720.96 516.401,1720.96 516.683,1720.96 516.401,1720.96 "/>
<path clip-path="url(#clip322)" d="M516.683 1720.96 L516.683 1720.96 L516.964 1720.96 L516.964 1720.96 L516.683 1720.96 L516.683 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="516.683,1720.96 516.683,1720.96 516.964,1720.96 516.683,1720.96 "/>
<path clip-path="url(#clip322)" d="M516.964 1720.96 L516.964 1720.96 L517.246 1720.96 L517.246 1720.96 L516.964 1720.96 L516.964 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="516.964,1720.96 516.964,1720.96 517.246,1720.96 516.964,1720.96 "/>
<path clip-path="url(#clip322)" d="M517.246 1720.96 L517.246 1720.96 L517.528 1720.96 L517.528 1720.96 L517.246 1720.96 L517.246 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="517.246,1720.96 517.246,1720.96 517.528,1720.96 517.246,1720.96 "/>
<path clip-path="url(#clip322)" d="M517.528 1720.96 L517.528 1720.96 L517.809 1720.96 L517.809 1720.96 L517.528 1720.96 L517.528 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="517.528,1720.96 517.528,1720.96 517.809,1720.96 517.528,1720.96 "/>
<path clip-path="url(#clip322)" d="M517.809 1720.96 L517.809 1720.96 L518.091 1720.96 L518.091 1720.96 L517.809 1720.96 L517.809 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="517.809,1720.96 517.809,1720.96 518.091,1720.96 517.809,1720.96 "/>
<path clip-path="url(#clip322)" d="M518.091 1720.96 L518.091 1720.96 L518.373 1720.96 L518.373 1720.96 L518.091 1720.96 L518.091 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="518.091,1720.96 518.091,1720.96 518.373,1720.96 518.091,1720.96 "/>
<path clip-path="url(#clip322)" d="M518.373 1720.96 L518.373 1720.96 L518.655 1720.96 L518.655 1720.96 L518.373 1720.96 L518.373 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="518.373,1720.96 518.373,1720.96 518.655,1720.96 518.373,1720.96 "/>
<path clip-path="url(#clip322)" d="M518.655 1720.96 L518.655 1720.96 L518.936 1720.96 L518.936 1720.96 L518.655 1720.96 L518.655 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="518.655,1720.96 518.655,1720.96 518.936,1720.96 518.655,1720.96 "/>
<path clip-path="url(#clip322)" d="M518.936 1720.96 L518.936 1720.96 L519.218 1720.96 L519.218 1720.96 L518.936 1720.96 L518.936 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="518.936,1720.96 518.936,1720.96 519.218,1720.96 518.936,1720.96 "/>
<path clip-path="url(#clip322)" d="M519.218 1720.96 L519.218 1720.96 L519.5 1720.96 L519.5 1720.96 L519.218 1720.96 L519.218 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="519.218,1720.96 519.218,1720.96 519.5,1720.96 519.218,1720.96 "/>
<path clip-path="url(#clip322)" d="M519.5 1720.96 L519.5 1720.96 L519.782 1720.96 L519.782 1720.96 L519.5 1720.96 L519.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="519.5,1720.96 519.5,1720.96 519.782,1720.96 519.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M519.782 1720.96 L519.782 1720.96 L520.063 1720.96 L520.063 1720.96 L519.782 1720.96 L519.782 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="519.782,1720.96 519.782,1720.96 520.063,1720.96 519.782,1720.96 "/>
<path clip-path="url(#clip322)" d="M520.063 1720.96 L520.063 1720.96 L520.345 1720.96 L520.345 1720.96 L520.063 1720.96 L520.063 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="520.063,1720.96 520.063,1720.96 520.345,1720.96 520.063,1720.96 "/>
<path clip-path="url(#clip322)" d="M520.345 1720.96 L520.345 1720.96 L520.627 1720.96 L520.627 1720.96 L520.345 1720.96 L520.345 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="520.345,1720.96 520.345,1720.96 520.627,1720.96 520.345,1720.96 "/>
<path clip-path="url(#clip322)" d="M520.627 1720.96 L520.627 1720.96 L520.908 1720.96 L520.908 1720.96 L520.627 1720.96 L520.627 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="520.627,1720.96 520.627,1720.96 520.908,1720.96 520.627,1720.96 "/>
<path clip-path="url(#clip322)" d="M520.908 1720.96 L520.908 1720.96 L521.19 1720.96 L521.19 1720.96 L520.908 1720.96 L520.908 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="520.908,1720.96 520.908,1720.96 521.19,1720.96 520.908,1720.96 "/>
<path clip-path="url(#clip322)" d="M521.19 1720.96 L521.19 1720.96 L521.472 1720.96 L521.472 1720.96 L521.19 1720.96 L521.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="521.19,1720.96 521.19,1720.96 521.472,1720.96 521.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M521.472 1720.96 L521.472 1720.96 L521.754 1720.96 L521.754 1720.96 L521.472 1720.96 L521.472 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="521.472,1720.96 521.472,1720.96 521.754,1720.96 521.472,1720.96 "/>
<path clip-path="url(#clip322)" d="M521.754 1720.96 L521.754 1720.96 L522.035 1720.96 L522.035 1720.96 L521.754 1720.96 L521.754 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="521.754,1720.96 521.754,1720.96 522.035,1720.96 521.754,1720.96 "/>
<path clip-path="url(#clip322)" d="M522.035 1720.96 L522.035 1720.96 L522.317 1720.96 L522.317 1720.96 L522.035 1720.96 L522.035 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="522.035,1720.96 522.035,1720.96 522.317,1720.96 522.035,1720.96 "/>
<path clip-path="url(#clip322)" d="M522.317 1720.96 L522.317 1720.96 L522.599 1720.96 L522.599 1720.96 L522.317 1720.96 L522.317 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="522.317,1720.96 522.317,1720.96 522.599,1720.96 522.317,1720.96 "/>
<path clip-path="url(#clip322)" d="M522.599 1720.96 L522.599 1720.96 L522.881 1720.96 L522.881 1720.96 L522.599 1720.96 L522.599 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="522.599,1720.96 522.599,1720.96 522.881,1720.96 522.599,1720.96 "/>
<path clip-path="url(#clip322)" d="M522.881 1720.96 L522.881 1720.96 L523.162 1720.96 L523.162 1720.96 L522.881 1720.96 L522.881 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="522.881,1720.96 522.881,1720.96 523.162,1720.96 522.881,1720.96 "/>
<path clip-path="url(#clip322)" d="M523.162 1720.96 L523.162 1720.96 L523.444 1720.96 L523.444 1720.96 L523.162 1720.96 L523.162 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="523.162,1720.96 523.162,1720.96 523.444,1720.96 523.162,1720.96 "/>
<path clip-path="url(#clip322)" d="M523.444 1720.96 L523.444 1720.96 L523.726 1720.96 L523.726 1720.96 L523.444 1720.96 L523.444 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="523.444,1720.96 523.444,1720.96 523.726,1720.96 523.444,1720.96 "/>
<path clip-path="url(#clip322)" d="M523.726 1720.96 L523.726 1720.96 L524.007 1720.96 L524.007 1720.96 L523.726 1720.96 L523.726 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="523.726,1720.96 523.726,1720.96 524.007,1720.96 523.726,1720.96 "/>
<path clip-path="url(#clip322)" d="M524.007 1720.96 L524.007 1720.96 L524.289 1720.96 L524.289 1720.96 L524.007 1720.96 L524.007 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="524.007,1720.96 524.007,1720.96 524.289,1720.96 524.007,1720.96 "/>
<path clip-path="url(#clip322)" d="M524.289 1720.96 L524.289 1720.96 L524.571 1720.96 L524.571 1720.96 L524.289 1720.96 L524.289 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="524.289,1720.96 524.289,1720.96 524.571,1720.96 524.289,1720.96 "/>
<path clip-path="url(#clip322)" d="M524.571 1720.96 L524.571 1720.96 L524.853 1720.96 L524.853 1720.96 L524.571 1720.96 L524.571 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="524.571,1720.96 524.571,1720.96 524.853,1720.96 524.571,1720.96 "/>
<path clip-path="url(#clip322)" d="M524.853 1720.96 L524.853 1720.96 L525.134 1720.96 L525.134 1720.96 L524.853 1720.96 L524.853 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="524.853,1720.96 524.853,1720.96 525.134,1720.96 524.853,1720.96 "/>
<path clip-path="url(#clip322)" d="M525.134 1720.96 L525.134 1720.96 L525.416 1720.96 L525.416 1720.96 L525.134 1720.96 L525.134 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="525.134,1720.96 525.134,1720.96 525.416,1720.96 525.134,1720.96 "/>
<path clip-path="url(#clip322)" d="M525.416 1720.96 L525.416 1720.96 L525.698 1720.96 L525.698 1720.96 L525.416 1720.96 L525.416 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="525.416,1720.96 525.416,1720.96 525.698,1720.96 525.416,1720.96 "/>
<path clip-path="url(#clip322)" d="M525.698 1720.96 L525.698 1720.96 L525.98 1720.96 L525.98 1720.96 L525.698 1720.96 L525.698 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="525.698,1720.96 525.698,1720.96 525.98,1720.96 525.698,1720.96 "/>
<path clip-path="url(#clip322)" d="M525.98 1720.96 L525.98 1720.96 L526.261 1720.96 L526.261 1720.96 L525.98 1720.96 L525.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="525.98,1720.96 525.98,1720.96 526.261,1720.96 525.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M526.261 1720.96 L526.261 1720.96 L526.543 1720.96 L526.543 1720.96 L526.261 1720.96 L526.261 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="526.261,1720.96 526.261,1720.96 526.543,1720.96 526.261,1720.96 "/>
<path clip-path="url(#clip322)" d="M526.543 1720.96 L526.543 1720.96 L526.825 1720.96 L526.825 1720.96 L526.543 1720.96 L526.543 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="526.543,1720.96 526.543,1720.96 526.825,1720.96 526.543,1720.96 "/>
<path clip-path="url(#clip322)" d="M526.825 1720.96 L526.825 1720.96 L527.106 1720.96 L527.106 1720.96 L526.825 1720.96 L526.825 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="526.825,1720.96 526.825,1720.96 527.106,1720.96 526.825,1720.96 "/>
<path clip-path="url(#clip322)" d="M527.106 1720.96 L527.106 1720.96 L527.388 1720.96 L527.388 1720.96 L527.106 1720.96 L527.106 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="527.106,1720.96 527.106,1720.96 527.388,1720.96 527.106,1720.96 "/>
<path clip-path="url(#clip322)" d="M527.388 1720.96 L527.388 1720.96 L527.67 1720.96 L527.67 1720.96 L527.388 1720.96 L527.388 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="527.388,1720.96 527.388,1720.96 527.67,1720.96 527.388,1720.96 "/>
<path clip-path="url(#clip322)" d="M527.67 1720.96 L527.67 1720.96 L527.952 1720.96 L527.952 1720.96 L527.67 1720.96 L527.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="527.67,1720.96 527.67,1720.96 527.952,1720.96 527.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M527.952 1720.96 L527.952 1720.96 L528.233 1720.96 L528.233 1720.96 L527.952 1720.96 L527.952 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="527.952,1720.96 527.952,1720.96 528.233,1720.96 527.952,1720.96 "/>
<path clip-path="url(#clip322)" d="M528.233 1720.96 L528.233 1720.96 L528.515 1720.96 L528.515 1720.96 L528.233 1720.96 L528.233 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="528.233,1720.96 528.233,1720.96 528.515,1720.96 528.233,1720.96 "/>
<path clip-path="url(#clip322)" d="M528.515 1720.96 L528.515 1720.96 L528.797 1720.96 L528.797 1720.96 L528.515 1720.96 L528.515 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="528.515,1720.96 528.515,1720.96 528.797,1720.96 528.515,1720.96 "/>
<path clip-path="url(#clip322)" d="M528.797 1720.96 L528.797 1720.96 L529.079 1720.96 L529.079 1720.96 L528.797 1720.96 L528.797 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="528.797,1720.96 528.797,1720.96 529.079,1720.96 528.797,1720.96 "/>
<path clip-path="url(#clip322)" d="M529.079 1720.96 L529.079 1720.96 L529.36 1720.96 L529.36 1720.96 L529.079 1720.96 L529.079 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="529.079,1720.96 529.079,1720.96 529.36,1720.96 529.079,1720.96 "/>
<path clip-path="url(#clip322)" d="M529.36 1720.96 L529.36 1720.96 L529.642 1720.96 L529.642 1720.96 L529.36 1720.96 L529.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="529.36,1720.96 529.36,1720.96 529.642,1720.96 529.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M529.642 1720.96 L529.642 1720.96 L529.924 1720.96 L529.924 1720.96 L529.642 1720.96 L529.642 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="529.642,1720.96 529.642,1720.96 529.924,1720.96 529.642,1720.96 "/>
<path clip-path="url(#clip322)" d="M529.924 1720.96 L529.924 1720.96 L530.205 1720.96 L530.205 1720.96 L529.924 1720.96 L529.924 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="529.924,1720.96 529.924,1720.96 530.205,1720.96 529.924,1720.96 "/>
<path clip-path="url(#clip322)" d="M530.205 1720.96 L530.205 1720.96 L530.487 1720.96 L530.487 1720.96 L530.205 1720.96 L530.205 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="530.205,1720.96 530.205,1720.96 530.487,1720.96 530.205,1720.96 "/>
<path clip-path="url(#clip322)" d="M530.487 1720.96 L530.487 1720.96 L530.769 1720.96 L530.769 1720.96 L530.487 1720.96 L530.487 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="530.487,1720.96 530.487,1720.96 530.769,1720.96 530.487,1720.96 "/>
<path clip-path="url(#clip322)" d="M530.769 1720.96 L530.769 1720.96 L531.051 1720.96 L531.051 1720.96 L530.769 1720.96 L530.769 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="530.769,1720.96 530.769,1720.96 531.051,1720.96 530.769,1720.96 "/>
<path clip-path="url(#clip322)" d="M531.051 1720.96 L531.051 1720.96 L531.332 1720.96 L531.332 1720.96 L531.051 1720.96 L531.051 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="531.051,1720.96 531.051,1720.96 531.332,1720.96 531.051,1720.96 "/>
<path clip-path="url(#clip322)" d="M531.332 1720.96 L531.332 1720.96 L531.614 1720.96 L531.614 1720.96 L531.332 1720.96 L531.332 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="531.332,1720.96 531.332,1720.96 531.614,1720.96 531.332,1720.96 "/>
<path clip-path="url(#clip322)" d="M531.614 1720.96 L531.614 1720.96 L531.896 1720.96 L531.896 1720.96 L531.614 1720.96 L531.614 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="531.614,1720.96 531.614,1720.96 531.896,1720.96 531.614,1720.96 "/>
<path clip-path="url(#clip322)" d="M531.896 1720.96 L531.896 1720.96 L532.177 1720.96 L532.177 1720.96 L531.896 1720.96 L531.896 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="531.896,1720.96 531.896,1720.96 532.177,1720.96 531.896,1720.96 "/>
<path clip-path="url(#clip322)" d="M532.177 1720.96 L532.177 1720.96 L532.459 1720.96 L532.459 1720.96 L532.177 1720.96 L532.177 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="532.177,1720.96 532.177,1720.96 532.459,1720.96 532.177,1720.96 "/>
<path clip-path="url(#clip322)" d="M532.459 1720.96 L532.459 1720.96 L532.741 1720.96 L532.741 1720.96 L532.459 1720.96 L532.459 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="532.459,1720.96 532.459,1720.96 532.741,1720.96 532.459,1720.96 "/>
<path clip-path="url(#clip322)" d="M532.741 1720.96 L532.741 1720.96 L533.023 1720.96 L533.023 1720.96 L532.741 1720.96 L532.741 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="532.741,1720.96 532.741,1720.96 533.023,1720.96 532.741,1720.96 "/>
<path clip-path="url(#clip322)" d="M533.023 1720.96 L533.023 1720.96 L533.304 1720.96 L533.304 1720.96 L533.023 1720.96 L533.023 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="533.023,1720.96 533.023,1720.96 533.304,1720.96 533.023,1720.96 "/>
<path clip-path="url(#clip322)" d="M533.304 1720.96 L533.304 1720.96 L533.586 1720.96 L533.586 1720.96 L533.304 1720.96 L533.304 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="533.304,1720.96 533.304,1720.96 533.586,1720.96 533.304,1720.96 "/>
<path clip-path="url(#clip322)" d="M533.586 1720.96 L533.586 1720.96 L533.868 1720.96 L533.868 1720.96 L533.586 1720.96 L533.586 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="533.586,1720.96 533.586,1720.96 533.868,1720.96 533.586,1720.96 "/>
<path clip-path="url(#clip322)" d="M533.868 1720.96 L533.868 1720.96 L534.15 1720.96 L534.15 1720.96 L533.868 1720.96 L533.868 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="533.868,1720.96 533.868,1720.96 534.15,1720.96 533.868,1720.96 "/>
<path clip-path="url(#clip322)" d="M534.15 1720.96 L534.15 1720.96 L534.431 1720.96 L534.431 1720.96 L534.15 1720.96 L534.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="534.15,1720.96 534.15,1720.96 534.431,1720.96 534.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M534.431 1720.96 L534.431 1720.96 L534.713 1720.96 L534.713 1720.96 L534.431 1720.96 L534.431 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="534.431,1720.96 534.431,1720.96 534.713,1720.96 534.431,1720.96 "/>
<path clip-path="url(#clip322)" d="M534.713 1720.96 L534.713 1720.96 L534.995 1720.96 L534.995 1720.96 L534.713 1720.96 L534.713 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="534.713,1720.96 534.713,1720.96 534.995,1720.96 534.713,1720.96 "/>
<path clip-path="url(#clip322)" d="M534.995 1720.96 L534.995 1720.96 L535.276 1720.96 L535.276 1720.96 L534.995 1720.96 L534.995 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="534.995,1720.96 534.995,1720.96 535.276,1720.96 534.995,1720.96 "/>
<path clip-path="url(#clip322)" d="M535.276 1720.96 L535.276 1720.96 L535.558 1720.96 L535.558 1720.96 L535.276 1720.96 L535.276 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="535.276,1720.96 535.276,1720.96 535.558,1720.96 535.276,1720.96 "/>
<path clip-path="url(#clip322)" d="M535.558 1720.96 L535.558 1720.96 L535.84 1720.96 L535.84 1720.96 L535.558 1720.96 L535.558 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="535.558,1720.96 535.558,1720.96 535.84,1720.96 535.558,1720.96 "/>
<path clip-path="url(#clip322)" d="M535.84 1720.96 L535.84 1720.96 L536.122 1720.96 L536.122 1720.96 L535.84 1720.96 L535.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="535.84,1720.96 535.84,1720.96 536.122,1720.96 535.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M536.122 1720.96 L536.122 1720.96 L536.403 1720.96 L536.403 1720.96 L536.122 1720.96 L536.122 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="536.122,1720.96 536.122,1720.96 536.403,1720.96 536.122,1720.96 "/>
<path clip-path="url(#clip322)" d="M536.403 1720.96 L536.403 1720.96 L536.685 1720.96 L536.685 1720.96 L536.403 1720.96 L536.403 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="536.403,1720.96 536.403,1720.96 536.685,1720.96 536.403,1720.96 "/>
<path clip-path="url(#clip322)" d="M536.685 1720.96 L536.685 1720.96 L536.967 1720.96 L536.967 1720.96 L536.685 1720.96 L536.685 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="536.685,1720.96 536.685,1720.96 536.967,1720.96 536.685,1720.96 "/>
<path clip-path="url(#clip322)" d="M536.967 1720.96 L536.967 1720.96 L537.249 1720.96 L537.249 1720.96 L536.967 1720.96 L536.967 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="536.967,1720.96 536.967,1720.96 537.249,1720.96 536.967,1720.96 "/>
<path clip-path="url(#clip322)" d="M537.249 1720.96 L537.249 1720.96 L537.53 1720.96 L537.53 1720.96 L537.249 1720.96 L537.249 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="537.249,1720.96 537.249,1720.96 537.53,1720.96 537.249,1720.96 "/>
<path clip-path="url(#clip322)" d="M537.53 1720.96 L537.53 1720.96 L537.812 1720.96 L537.812 1720.96 L537.53 1720.96 L537.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="537.53,1720.96 537.53,1720.96 537.812,1720.96 537.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M537.812 1720.96 L537.812 1720.96 L538.094 1720.96 L538.094 1720.96 L537.812 1720.96 L537.812 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="537.812,1720.96 537.812,1720.96 538.094,1720.96 537.812,1720.96 "/>
<path clip-path="url(#clip322)" d="M538.094 1720.96 L538.094 1720.96 L538.375 1720.96 L538.375 1720.96 L538.094 1720.96 L538.094 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="538.094,1720.96 538.094,1720.96 538.375,1720.96 538.094,1720.96 "/>
<path clip-path="url(#clip322)" d="M538.375 1720.96 L538.375 1720.96 L538.657 1720.96 L538.657 1720.96 L538.375 1720.96 L538.375 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="538.375,1720.96 538.375,1720.96 538.657,1720.96 538.375,1720.96 "/>
<path clip-path="url(#clip322)" d="M538.657 1720.96 L538.657 1720.96 L538.939 1720.96 L538.939 1720.96 L538.657 1720.96 L538.657 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="538.657,1720.96 538.657,1720.96 538.939,1720.96 538.657,1720.96 "/>
<path clip-path="url(#clip322)" d="M538.939 1720.96 L538.939 1720.96 L539.221 1720.96 L539.221 1720.96 L538.939 1720.96 L538.939 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="538.939,1720.96 538.939,1720.96 539.221,1720.96 538.939,1720.96 "/>
<path clip-path="url(#clip322)" d="M539.221 1720.96 L539.221 1720.96 L539.502 1720.96 L539.502 1720.96 L539.221 1720.96 L539.221 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="539.221,1720.96 539.221,1720.96 539.502,1720.96 539.221,1720.96 "/>
<path clip-path="url(#clip322)" d="M539.502 1720.96 L539.502 1720.96 L539.784 1720.96 L539.784 1720.96 L539.502 1720.96 L539.502 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="539.502,1720.96 539.502,1720.96 539.784,1720.96 539.502,1720.96 "/>
<path clip-path="url(#clip322)" d="M539.784 1720.96 L539.784 1720.96 L540.066 1720.96 L540.066 1720.96 L539.784 1720.96 L539.784 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="539.784,1720.96 539.784,1720.96 540.066,1720.96 539.784,1720.96 "/>
<path clip-path="url(#clip322)" d="M540.066 1720.96 L540.066 1720.96 L540.348 1720.96 L540.348 1720.96 L540.066 1720.96 L540.066 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="540.066,1720.96 540.066,1720.96 540.348,1720.96 540.066,1720.96 "/>
<path clip-path="url(#clip322)" d="M540.348 1720.96 L540.348 1720.96 L540.629 1720.96 L540.629 1720.96 L540.348 1720.96 L540.348 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="540.348,1720.96 540.348,1720.96 540.629,1720.96 540.348,1720.96 "/>
<path clip-path="url(#clip322)" d="M540.629 1720.96 L540.629 1720.96 L540.911 1720.96 L540.911 1720.96 L540.629 1720.96 L540.629 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="540.629,1720.96 540.629,1720.96 540.911,1720.96 540.629,1720.96 "/>
<path clip-path="url(#clip322)" d="M540.911 1720.96 L540.911 1720.96 L541.193 1720.96 L541.193 1720.96 L540.911 1720.96 L540.911 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="540.911,1720.96 540.911,1720.96 541.193,1720.96 540.911,1720.96 "/>
<path clip-path="url(#clip322)" d="M541.193 1720.96 L541.193 1720.96 L541.474 1720.96 L541.474 1720.96 L541.193 1720.96 L541.193 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="541.193,1720.96 541.193,1720.96 541.474,1720.96 541.193,1720.96 "/>
<path clip-path="url(#clip322)" d="M541.474 1720.96 L541.474 1720.96 L541.756 1720.96 L541.756 1720.96 L541.474 1720.96 L541.474 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="541.474,1720.96 541.474,1720.96 541.756,1720.96 541.474,1720.96 "/>
<path clip-path="url(#clip322)" d="M541.756 1720.96 L541.756 1720.96 L542.038 1720.96 L542.038 1720.96 L541.756 1720.96 L541.756 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="541.756,1720.96 541.756,1720.96 542.038,1720.96 541.756,1720.96 "/>
<path clip-path="url(#clip322)" d="M542.038 1720.96 L542.038 1720.96 L542.32 1720.96 L542.32 1720.96 L542.038 1720.96 L542.038 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="542.038,1720.96 542.038,1720.96 542.32,1720.96 542.038,1720.96 "/>
<path clip-path="url(#clip322)" d="M542.32 1720.96 L542.32 1720.96 L542.601 1720.96 L542.601 1720.96 L542.32 1720.96 L542.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="542.32,1720.96 542.32,1720.96 542.601,1720.96 542.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M542.601 1720.96 L542.601 1720.96 L542.883 1720.96 L542.883 1720.96 L542.601 1720.96 L542.601 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="542.601,1720.96 542.601,1720.96 542.883,1720.96 542.601,1720.96 "/>
<path clip-path="url(#clip322)" d="M542.883 1720.96 L542.883 1720.96 L543.165 1720.96 L543.165 1720.96 L542.883 1720.96 L542.883 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="542.883,1720.96 542.883,1720.96 543.165,1720.96 542.883,1720.96 "/>
<path clip-path="url(#clip322)" d="M543.165 1720.96 L543.165 1720.96 L543.447 1720.96 L543.447 1720.96 L543.165 1720.96 L543.165 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="543.165,1720.96 543.165,1720.96 543.447,1720.96 543.165,1720.96 "/>
<path clip-path="url(#clip322)" d="M543.447 1720.96 L543.447 1720.96 L543.728 1720.96 L543.728 1720.96 L543.447 1720.96 L543.447 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="543.447,1720.96 543.447,1720.96 543.728,1720.96 543.447,1720.96 "/>
<path clip-path="url(#clip322)" d="M543.728 1720.96 L543.728 1720.96 L544.01 1720.96 L544.01 1720.96 L543.728 1720.96 L543.728 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="543.728,1720.96 543.728,1720.96 544.01,1720.96 543.728,1720.96 "/>
<path clip-path="url(#clip322)" d="M544.01 1720.96 L544.01 1720.96 L544.292 1720.96 L544.292 1720.96 L544.01 1720.96 L544.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="544.01,1720.96 544.01,1720.96 544.292,1720.96 544.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M544.292 1720.96 L544.292 1720.96 L544.573 1720.96 L544.573 1720.96 L544.292 1720.96 L544.292 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="544.292,1720.96 544.292,1720.96 544.573,1720.96 544.292,1720.96 "/>
<path clip-path="url(#clip322)" d="M544.573 1720.96 L544.573 1720.96 L544.855 1720.96 L544.855 1720.96 L544.573 1720.96 L544.573 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="544.573,1720.96 544.573,1720.96 544.855,1720.96 544.573,1720.96 "/>
<path clip-path="url(#clip322)" d="M544.855 1720.96 L544.855 1720.96 L545.137 1720.96 L545.137 1720.96 L544.855 1720.96 L544.855 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="544.855,1720.96 544.855,1720.96 545.137,1720.96 544.855,1720.96 "/>
<path clip-path="url(#clip322)" d="M545.137 1720.96 L545.137 1720.96 L545.419 1720.96 L545.419 1720.96 L545.137 1720.96 L545.137 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="545.137,1720.96 545.137,1720.96 545.419,1720.96 545.137,1720.96 "/>
<path clip-path="url(#clip322)" d="M545.419 1720.96 L545.419 1720.96 L545.7 1720.96 L545.7 1720.96 L545.419 1720.96 L545.419 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="545.419,1720.96 545.419,1720.96 545.7,1720.96 545.419,1720.96 "/>
<path clip-path="url(#clip322)" d="M545.7 1720.96 L545.7 1720.96 L545.982 1720.96 L545.982 1720.96 L545.7 1720.96 L545.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="545.7,1720.96 545.7,1720.96 545.982,1720.96 545.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M545.982 1720.96 L545.982 1720.96 L546.264 1720.96 L546.264 1720.96 L545.982 1720.96 L545.982 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="545.982,1720.96 545.982,1720.96 546.264,1720.96 545.982,1720.96 "/>
<path clip-path="url(#clip322)" d="M546.264 1720.96 L546.264 1720.96 L546.545 1720.96 L546.545 1720.96 L546.264 1720.96 L546.264 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="546.264,1720.96 546.264,1720.96 546.545,1720.96 546.264,1720.96 "/>
<path clip-path="url(#clip322)" d="M546.545 1720.96 L546.545 1720.96 L546.827 1720.96 L546.827 1720.96 L546.545 1720.96 L546.545 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="546.545,1720.96 546.545,1720.96 546.827,1720.96 546.545,1720.96 "/>
<path clip-path="url(#clip322)" d="M546.827 1720.96 L546.827 1720.96 L547.109 1720.96 L547.109 1720.96 L546.827 1720.96 L546.827 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="546.827,1720.96 546.827,1720.96 547.109,1720.96 546.827,1720.96 "/>
<path clip-path="url(#clip322)" d="M547.109 1720.96 L547.109 1720.96 L547.391 1720.96 L547.391 1720.96 L547.109 1720.96 L547.109 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="547.109,1720.96 547.109,1720.96 547.391,1720.96 547.109,1720.96 "/>
<path clip-path="url(#clip322)" d="M547.391 1720.96 L547.391 1720.96 L547.672 1720.96 L547.672 1720.96 L547.391 1720.96 L547.391 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="547.391,1720.96 547.391,1720.96 547.672,1720.96 547.391,1720.96 "/>
<path clip-path="url(#clip322)" d="M547.672 1720.96 L547.672 1720.96 L547.954 1720.96 L547.954 1720.96 L547.672 1720.96 L547.672 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="547.672,1720.96 547.672,1720.96 547.954,1720.96 547.672,1720.96 "/>
<path clip-path="url(#clip322)" d="M547.954 1720.96 L547.954 1720.96 L548.236 1720.96 L548.236 1720.96 L547.954 1720.96 L547.954 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="547.954,1720.96 547.954,1720.96 548.236,1720.96 547.954,1720.96 "/>
<path clip-path="url(#clip322)" d="M548.236 1720.96 L548.236 1720.96 L548.518 1720.96 L548.518 1720.96 L548.236 1720.96 L548.236 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="548.236,1720.96 548.236,1720.96 548.518,1720.96 548.236,1720.96 "/>
<path clip-path="url(#clip322)" d="M548.518 1720.96 L548.518 1720.96 L548.799 1720.96 L548.799 1720.96 L548.518 1720.96 L548.518 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="548.518,1720.96 548.518,1720.96 548.799,1720.96 548.518,1720.96 "/>
<path clip-path="url(#clip322)" d="M548.799 1720.96 L548.799 1720.96 L549.081 1720.96 L549.081 1720.96 L548.799 1720.96 L548.799 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="548.799,1720.96 548.799,1720.96 549.081,1720.96 548.799,1720.96 "/>
<path clip-path="url(#clip322)" d="M549.081 1720.96 L549.081 1720.96 L549.363 1720.96 L549.363 1720.96 L549.081 1720.96 L549.081 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="549.081,1720.96 549.081,1720.96 549.363,1720.96 549.081,1720.96 "/>
<path clip-path="url(#clip322)" d="M549.363 1720.96 L549.363 1720.96 L549.644 1720.96 L549.644 1720.96 L549.363 1720.96 L549.363 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="549.363,1720.96 549.363,1720.96 549.644,1720.96 549.363,1720.96 "/>
<path clip-path="url(#clip322)" d="M549.644 1720.96 L549.644 1720.96 L549.926 1720.96 L549.926 1720.96 L549.644 1720.96 L549.644 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="549.644,1720.96 549.644,1720.96 549.926,1720.96 549.644,1720.96 "/>
<path clip-path="url(#clip322)" d="M549.926 1720.96 L549.926 1720.96 L550.208 1720.96 L550.208 1720.96 L549.926 1720.96 L549.926 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="549.926,1720.96 549.926,1720.96 550.208,1720.96 549.926,1720.96 "/>
<path clip-path="url(#clip322)" d="M550.208 1720.96 L550.208 1720.96 L550.49 1720.96 L550.49 1720.96 L550.208 1720.96 L550.208 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="550.208,1720.96 550.208,1720.96 550.49,1720.96 550.208,1720.96 "/>
<path clip-path="url(#clip322)" d="M550.49 1720.96 L550.49 1720.96 L550.771 1720.96 L550.771 1720.96 L550.49 1720.96 L550.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="550.49,1720.96 550.49,1720.96 550.771,1720.96 550.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M550.771 1720.96 L550.771 1720.96 L551.053 1720.96 L551.053 1720.96 L550.771 1720.96 L550.771 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="550.771,1720.96 550.771,1720.96 551.053,1720.96 550.771,1720.96 "/>
<path clip-path="url(#clip322)" d="M551.053 1720.96 L551.053 1720.96 L551.335 1720.96 L551.335 1720.96 L551.053 1720.96 L551.053 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="551.053,1720.96 551.053,1720.96 551.335,1720.96 551.053,1720.96 "/>
<path clip-path="url(#clip322)" d="M551.335 1720.96 L551.335 1720.96 L551.617 1720.96 L551.617 1720.96 L551.335 1720.96 L551.335 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="551.335,1720.96 551.335,1720.96 551.617,1720.96 551.335,1720.96 "/>
<path clip-path="url(#clip322)" d="M551.617 1720.96 L551.617 1720.96 L551.898 1720.96 L551.898 1720.96 L551.617 1720.96 L551.617 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="551.617,1720.96 551.617,1720.96 551.898,1720.96 551.617,1720.96 "/>
<path clip-path="url(#clip322)" d="M551.898 1720.96 L551.898 1720.96 L552.18 1720.96 L552.18 1720.96 L551.898 1720.96 L551.898 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="551.898,1720.96 551.898,1720.96 552.18,1720.96 551.898,1720.96 "/>
<path clip-path="url(#clip322)" d="M552.18 1720.96 L552.18 1720.96 L552.462 1720.96 L552.462 1720.96 L552.18 1720.96 L552.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="552.18,1720.96 552.18,1720.96 552.462,1720.96 552.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M552.462 1720.96 L552.462 1720.96 L552.743 1720.96 L552.743 1720.96 L552.462 1720.96 L552.462 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="552.462,1720.96 552.462,1720.96 552.743,1720.96 552.462,1720.96 "/>
<path clip-path="url(#clip322)" d="M552.743 1720.96 L552.743 1720.96 L553.025 1720.96 L553.025 1720.96 L552.743 1720.96 L552.743 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="552.743,1720.96 552.743,1720.96 553.025,1720.96 552.743,1720.96 "/>
<path clip-path="url(#clip322)" d="M553.025 1720.96 L553.025 1720.96 L553.307 1720.96 L553.307 1720.96 L553.025 1720.96 L553.025 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="553.025,1720.96 553.025,1720.96 553.307,1720.96 553.025,1720.96 "/>
<path clip-path="url(#clip322)" d="M553.307 1720.96 L553.307 1720.96 L553.589 1720.96 L553.589 1720.96 L553.307 1720.96 L553.307 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="553.307,1720.96 553.307,1720.96 553.589,1720.96 553.307,1720.96 "/>
<path clip-path="url(#clip322)" d="M553.589 1720.96 L553.589 1720.96 L553.87 1720.96 L553.87 1720.96 L553.589 1720.96 L553.589 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="553.589,1720.96 553.589,1720.96 553.87,1720.96 553.589,1720.96 "/>
<path clip-path="url(#clip322)" d="M553.87 1720.96 L553.87 1720.96 L554.152 1720.96 L554.152 1720.96 L553.87 1720.96 L553.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="553.87,1720.96 553.87,1720.96 554.152,1720.96 553.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M554.152 1720.96 L554.152 1720.96 L554.434 1720.96 L554.434 1720.96 L554.152 1720.96 L554.152 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="554.152,1720.96 554.152,1720.96 554.434,1720.96 554.152,1720.96 "/>
<path clip-path="url(#clip322)" d="M554.434 1720.96 L554.434 1720.96 L554.716 1720.96 L554.716 1720.96 L554.434 1720.96 L554.434 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="554.434,1720.96 554.434,1720.96 554.716,1720.96 554.434,1720.96 "/>
<path clip-path="url(#clip322)" d="M554.716 1720.96 L554.716 1720.96 L554.997 1720.96 L554.997 1720.96 L554.716 1720.96 L554.716 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="554.716,1720.96 554.716,1720.96 554.997,1720.96 554.716,1720.96 "/>
<path clip-path="url(#clip322)" d="M554.997 1720.96 L554.997 1720.96 L555.279 1720.96 L555.279 1720.96 L554.997 1720.96 L554.997 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="554.997,1720.96 554.997,1720.96 555.279,1720.96 554.997,1720.96 "/>
<path clip-path="url(#clip322)" d="M555.279 1720.96 L555.279 1720.96 L555.561 1720.96 L555.561 1720.96 L555.279 1720.96 L555.279 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="555.279,1720.96 555.279,1720.96 555.561,1720.96 555.279,1720.96 "/>
<path clip-path="url(#clip322)" d="M555.561 1720.96 L555.561 1720.96 L555.842 1720.96 L555.842 1720.96 L555.561 1720.96 L555.561 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="555.561,1720.96 555.561,1720.96 555.842,1720.96 555.561,1720.96 "/>
<path clip-path="url(#clip322)" d="M555.842 1720.96 L555.842 1720.96 L556.124 1720.96 L556.124 1720.96 L555.842 1720.96 L555.842 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="555.842,1720.96 555.842,1720.96 556.124,1720.96 555.842,1720.96 "/>
<path clip-path="url(#clip322)" d="M556.124 1720.96 L556.124 1720.96 L556.406 1720.96 L556.406 1720.96 L556.124 1720.96 L556.124 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="556.124,1720.96 556.124,1720.96 556.406,1720.96 556.124,1720.96 "/>
<path clip-path="url(#clip322)" d="M556.406 1720.96 L556.406 1720.96 L556.688 1720.96 L556.688 1720.96 L556.406 1720.96 L556.406 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="556.406,1720.96 556.406,1720.96 556.688,1720.96 556.406,1720.96 "/>
<path clip-path="url(#clip322)" d="M556.688 1720.96 L556.688 1720.96 L556.969 1720.96 L556.969 1720.96 L556.688 1720.96 L556.688 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="556.688,1720.96 556.688,1720.96 556.969,1720.96 556.688,1720.96 "/>
<path clip-path="url(#clip322)" d="M556.969 1720.96 L556.969 1720.96 L557.251 1720.96 L557.251 1720.96 L556.969 1720.96 L556.969 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="556.969,1720.96 556.969,1720.96 557.251,1720.96 556.969,1720.96 "/>
<path clip-path="url(#clip322)" d="M557.251 1720.96 L557.251 1720.96 L557.533 1720.96 L557.533 1720.96 L557.251 1720.96 L557.251 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="557.251,1720.96 557.251,1720.96 557.533,1720.96 557.251,1720.96 "/>
<path clip-path="url(#clip322)" d="M557.533 1720.96 L557.533 1720.96 L557.815 1720.96 L557.815 1720.96 L557.533 1720.96 L557.533 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="557.533,1720.96 557.533,1720.96 557.815,1720.96 557.533,1720.96 "/>
<path clip-path="url(#clip322)" d="M557.815 1720.96 L557.815 1720.96 L558.096 1720.96 L558.096 1720.96 L557.815 1720.96 L557.815 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="557.815,1720.96 557.815,1720.96 558.096,1720.96 557.815,1720.96 "/>
<path clip-path="url(#clip322)" d="M558.096 1720.96 L558.096 1720.96 L558.378 1720.96 L558.378 1720.96 L558.096 1720.96 L558.096 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="558.096,1720.96 558.096,1720.96 558.378,1720.96 558.096,1720.96 "/>
<path clip-path="url(#clip322)" d="M558.378 1720.96 L558.378 1720.96 L558.66 1720.96 L558.66 1720.96 L558.378 1720.96 L558.378 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="558.378,1720.96 558.378,1720.96 558.66,1720.96 558.378,1720.96 "/>
<path clip-path="url(#clip322)" d="M558.66 1720.96 L558.66 1720.96 L558.941 1720.96 L558.941 1720.96 L558.66 1720.96 L558.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="558.66,1720.96 558.66,1720.96 558.941,1720.96 558.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M558.941 1720.96 L558.941 1720.96 L559.223 1720.96 L559.223 1720.96 L558.941 1720.96 L558.941 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="558.941,1720.96 558.941,1720.96 559.223,1720.96 558.941,1720.96 "/>
<path clip-path="url(#clip322)" d="M559.223 1720.96 L559.223 1720.96 L559.505 1720.96 L559.505 1720.96 L559.223 1720.96 L559.223 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="559.223,1720.96 559.223,1720.96 559.505,1720.96 559.223,1720.96 "/>
<path clip-path="url(#clip322)" d="M559.505 1720.96 L559.505 1720.96 L559.787 1720.96 L559.787 1720.96 L559.505 1720.96 L559.505 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="559.505,1720.96 559.505,1720.96 559.787,1720.96 559.505,1720.96 "/>
<path clip-path="url(#clip322)" d="M559.787 1720.96 L559.787 1720.96 L560.068 1720.96 L560.068 1720.96 L559.787 1720.96 L559.787 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="559.787,1720.96 559.787,1720.96 560.068,1720.96 559.787,1720.96 "/>
<path clip-path="url(#clip322)" d="M560.068 1720.96 L560.068 1720.96 L560.35 1720.96 L560.35 1720.96 L560.068 1720.96 L560.068 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="560.068,1720.96 560.068,1720.96 560.35,1720.96 560.068,1720.96 "/>
<path clip-path="url(#clip322)" d="M560.35 1720.96 L560.35 1720.96 L560.632 1720.96 L560.632 1720.96 L560.35 1720.96 L560.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="560.35,1720.96 560.35,1720.96 560.632,1720.96 560.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M560.632 1720.96 L560.632 1720.96 L560.913 1720.96 L560.913 1720.96 L560.632 1720.96 L560.632 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="560.632,1720.96 560.632,1720.96 560.913,1720.96 560.632,1720.96 "/>
<path clip-path="url(#clip322)" d="M560.913 1720.96 L560.913 1720.96 L561.195 1720.96 L561.195 1720.96 L560.913 1720.96 L560.913 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="560.913,1720.96 560.913,1720.96 561.195,1720.96 560.913,1720.96 "/>
<path clip-path="url(#clip322)" d="M561.195 1720.96 L561.195 1720.96 L561.477 1720.96 L561.477 1720.96 L561.195 1720.96 L561.195 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="561.195,1720.96 561.195,1720.96 561.477,1720.96 561.195,1720.96 "/>
<path clip-path="url(#clip322)" d="M561.477 1720.96 L561.477 1720.96 L561.759 1720.96 L561.759 1720.96 L561.477 1720.96 L561.477 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="561.477,1720.96 561.477,1720.96 561.759,1720.96 561.477,1720.96 "/>
<path clip-path="url(#clip322)" d="M561.759 1720.96 L561.759 1720.96 L562.04 1720.96 L562.04 1720.96 L561.759 1720.96 L561.759 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="561.759,1720.96 561.759,1720.96 562.04,1720.96 561.759,1720.96 "/>
<path clip-path="url(#clip322)" d="M562.04 1720.96 L562.04 1720.96 L562.322 1720.96 L562.322 1720.96 L562.04 1720.96 L562.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="562.04,1720.96 562.04,1720.96 562.322,1720.96 562.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M562.322 1720.96 L562.322 1720.96 L562.604 1720.96 L562.604 1720.96 L562.322 1720.96 L562.322 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="562.322,1720.96 562.322,1720.96 562.604,1720.96 562.322,1720.96 "/>
<path clip-path="url(#clip322)" d="M562.604 1720.96 L562.604 1720.96 L562.886 1720.96 L562.886 1720.96 L562.604 1720.96 L562.604 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="562.604,1720.96 562.604,1720.96 562.886,1720.96 562.604,1720.96 "/>
<path clip-path="url(#clip322)" d="M562.886 1720.96 L562.886 1720.96 L563.167 1720.96 L563.167 1720.96 L562.886 1720.96 L562.886 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="562.886,1720.96 562.886,1720.96 563.167,1720.96 562.886,1720.96 "/>
<path clip-path="url(#clip322)" d="M563.167 1720.96 L563.167 1720.96 L563.449 1720.96 L563.449 1720.96 L563.167 1720.96 L563.167 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="563.167,1720.96 563.167,1720.96 563.449,1720.96 563.167,1720.96 "/>
<path clip-path="url(#clip322)" d="M563.449 1720.96 L563.449 1720.96 L563.731 1720.96 L563.731 1720.96 L563.449 1720.96 L563.449 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="563.449,1720.96 563.449,1720.96 563.731,1720.96 563.449,1720.96 "/>
<path clip-path="url(#clip322)" d="M563.731 1720.96 L563.731 1720.96 L564.012 1720.96 L564.012 1720.96 L563.731 1720.96 L563.731 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="563.731,1720.96 563.731,1720.96 564.012,1720.96 563.731,1720.96 "/>
<path clip-path="url(#clip322)" d="M564.012 1720.96 L564.012 1720.96 L564.294 1720.96 L564.294 1720.96 L564.012 1720.96 L564.012 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="564.012,1720.96 564.012,1720.96 564.294,1720.96 564.012,1720.96 "/>
<path clip-path="url(#clip322)" d="M564.294 1720.96 L564.294 1720.96 L564.576 1720.96 L564.576 1720.96 L564.294 1720.96 L564.294 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="564.294,1720.96 564.294,1720.96 564.576,1720.96 564.294,1720.96 "/>
<path clip-path="url(#clip322)" d="M564.576 1720.96 L564.576 1720.96 L564.858 1720.96 L564.858 1720.96 L564.576 1720.96 L564.576 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="564.576,1720.96 564.576,1720.96 564.858,1720.96 564.576,1720.96 "/>
<path clip-path="url(#clip322)" d="M564.858 1720.96 L564.858 1720.96 L565.139 1720.96 L565.139 1720.96 L564.858 1720.96 L564.858 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="564.858,1720.96 564.858,1720.96 565.139,1720.96 564.858,1720.96 "/>
<path clip-path="url(#clip322)" d="M565.139 1720.96 L565.139 1720.96 L565.421 1720.96 L565.421 1720.96 L565.139 1720.96 L565.139 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="565.139,1720.96 565.139,1720.96 565.421,1720.96 565.139,1720.96 "/>
<path clip-path="url(#clip322)" d="M565.421 1720.96 L565.421 1720.96 L565.703 1720.96 L565.703 1720.96 L565.421 1720.96 L565.421 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="565.421,1720.96 565.421,1720.96 565.703,1720.96 565.421,1720.96 "/>
<path clip-path="url(#clip322)" d="M565.703 1720.96 L565.703 1720.96 L565.985 1720.96 L565.985 1720.96 L565.703 1720.96 L565.703 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="565.703,1720.96 565.703,1720.96 565.985,1720.96 565.703,1720.96 "/>
<path clip-path="url(#clip322)" d="M565.985 1720.96 L565.985 1720.96 L566.266 1720.96 L566.266 1720.96 L565.985 1720.96 L565.985 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="565.985,1720.96 565.985,1720.96 566.266,1720.96 565.985,1720.96 "/>
<path clip-path="url(#clip322)" d="M566.266 1720.96 L566.266 1720.96 L566.548 1720.96 L566.548 1720.96 L566.266 1720.96 L566.266 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="566.266,1720.96 566.266,1720.96 566.548,1720.96 566.266,1720.96 "/>
<path clip-path="url(#clip322)" d="M566.548 1720.96 L566.548 1720.96 L566.83 1720.96 L566.83 1720.96 L566.548 1720.96 L566.548 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="566.548,1720.96 566.548,1720.96 566.83,1720.96 566.548,1720.96 "/>
<path clip-path="url(#clip322)" d="M566.83 1720.96 L566.83 1720.96 L567.111 1720.96 L567.111 1720.96 L566.83 1720.96 L566.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="566.83,1720.96 566.83,1720.96 567.111,1720.96 566.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M567.111 1720.96 L567.111 1720.96 L567.393 1720.96 L567.393 1720.96 L567.111 1720.96 L567.111 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="567.111,1720.96 567.111,1720.96 567.393,1720.96 567.111,1720.96 "/>
<path clip-path="url(#clip322)" d="M567.393 1720.96 L567.393 1720.96 L567.675 1720.96 L567.675 1720.96 L567.393 1720.96 L567.393 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="567.393,1720.96 567.393,1720.96 567.675,1720.96 567.393,1720.96 "/>
<path clip-path="url(#clip322)" d="M567.675 1720.96 L567.675 1720.96 L567.957 1720.96 L567.957 1720.96 L567.675 1720.96 L567.675 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="567.675,1720.96 567.675,1720.96 567.957,1720.96 567.675,1720.96 "/>
<path clip-path="url(#clip322)" d="M567.957 1720.96 L567.957 1720.96 L568.238 1720.96 L568.238 1720.96 L567.957 1720.96 L567.957 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="567.957,1720.96 567.957,1720.96 568.238,1720.96 567.957,1720.96 "/>
<path clip-path="url(#clip322)" d="M568.238 1720.96 L568.238 1720.96 L568.52 1720.96 L568.52 1720.96 L568.238 1720.96 L568.238 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="568.238,1720.96 568.238,1720.96 568.52,1720.96 568.238,1720.96 "/>
<path clip-path="url(#clip322)" d="M568.52 1720.96 L568.52 1720.96 L568.802 1720.96 L568.802 1720.96 L568.52 1720.96 L568.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="568.52,1720.96 568.52,1720.96 568.802,1720.96 568.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M568.802 1720.96 L568.802 1720.96 L569.084 1720.96 L569.084 1720.96 L568.802 1720.96 L568.802 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="568.802,1720.96 568.802,1720.96 569.084,1720.96 568.802,1720.96 "/>
<path clip-path="url(#clip322)" d="M569.084 1720.96 L569.084 1720.96 L569.365 1720.96 L569.365 1720.96 L569.084 1720.96 L569.084 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="569.084,1720.96 569.084,1720.96 569.365,1720.96 569.084,1720.96 "/>
<path clip-path="url(#clip322)" d="M569.365 1720.96 L569.365 1720.96 L569.647 1720.96 L569.647 1720.96 L569.365 1720.96 L569.365 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="569.365,1720.96 569.365,1720.96 569.647,1720.96 569.365,1720.96 "/>
<path clip-path="url(#clip322)" d="M569.647 1720.96 L569.647 1720.96 L569.929 1720.96 L569.929 1720.96 L569.647 1720.96 L569.647 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="569.647,1720.96 569.647,1720.96 569.929,1720.96 569.647,1720.96 "/>
<path clip-path="url(#clip322)" d="M569.929 1720.96 L569.929 1720.96 L570.21 1720.96 L570.21 1720.96 L569.929 1720.96 L569.929 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="569.929,1720.96 569.929,1720.96 570.21,1720.96 569.929,1720.96 "/>
<path clip-path="url(#clip322)" d="M570.21 1720.96 L570.21 1720.96 L570.492 1720.96 L570.492 1720.96 L570.21 1720.96 L570.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="570.21,1720.96 570.21,1720.96 570.492,1720.96 570.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M570.492 1720.96 L570.492 1720.96 L570.774 1720.96 L570.774 1720.96 L570.492 1720.96 L570.492 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="570.492,1720.96 570.492,1720.96 570.774,1720.96 570.492,1720.96 "/>
<path clip-path="url(#clip322)" d="M570.774 1720.96 L570.774 1720.96 L571.056 1720.96 L571.056 1720.96 L570.774 1720.96 L570.774 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="570.774,1720.96 570.774,1720.96 571.056,1720.96 570.774,1720.96 "/>
<path clip-path="url(#clip322)" d="M571.056 1720.96 L571.056 1720.96 L571.337 1720.96 L571.337 1720.96 L571.056 1720.96 L571.056 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="571.056,1720.96 571.056,1720.96 571.337,1720.96 571.056,1720.96 "/>
<path clip-path="url(#clip322)" d="M571.337 1720.96 L571.337 1720.96 L571.619 1720.96 L571.619 1720.96 L571.337 1720.96 L571.337 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="571.337,1720.96 571.337,1720.96 571.619,1720.96 571.337,1720.96 "/>
<path clip-path="url(#clip322)" d="M571.619 1720.96 L571.619 1720.96 L571.901 1720.96 L571.901 1720.96 L571.619 1720.96 L571.619 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="571.619,1720.96 571.619,1720.96 571.901,1720.96 571.619,1720.96 "/>
<path clip-path="url(#clip322)" d="M571.901 1720.96 L571.901 1720.96 L572.183 1720.96 L572.183 1720.96 L571.901 1720.96 L571.901 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="571.901,1720.96 571.901,1720.96 572.183,1720.96 571.901,1720.96 "/>
<path clip-path="url(#clip322)" d="M572.183 1720.96 L572.183 1720.96 L572.464 1720.96 L572.464 1720.96 L572.183 1720.96 L572.183 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="572.183,1720.96 572.183,1720.96 572.464,1720.96 572.183,1720.96 "/>
<path clip-path="url(#clip322)" d="M572.464 1720.96 L572.464 1720.96 L572.746 1720.96 L572.746 1720.96 L572.464 1720.96 L572.464 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="572.464,1720.96 572.464,1720.96 572.746,1720.96 572.464,1720.96 "/>
<path clip-path="url(#clip322)" d="M572.746 1720.96 L572.746 1720.96 L573.028 1720.96 L573.028 1720.96 L572.746 1720.96 L572.746 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="572.746,1720.96 572.746,1720.96 573.028,1720.96 572.746,1720.96 "/>
<path clip-path="url(#clip322)" d="M573.028 1720.96 L573.028 1720.96 L573.309 1720.96 L573.309 1720.96 L573.028 1720.96 L573.028 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="573.028,1720.96 573.028,1720.96 573.309,1720.96 573.028,1720.96 "/>
<path clip-path="url(#clip322)" d="M573.309 1720.96 L573.309 1720.96 L573.591 1720.96 L573.591 1720.96 L573.309 1720.96 L573.309 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="573.309,1720.96 573.309,1720.96 573.591,1720.96 573.309,1720.96 "/>
<path clip-path="url(#clip322)" d="M573.591 1720.96 L573.591 1720.96 L573.873 1720.96 L573.873 1720.96 L573.591 1720.96 L573.591 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="573.591,1720.96 573.591,1720.96 573.873,1720.96 573.591,1720.96 "/>
<path clip-path="url(#clip322)" d="M573.873 1720.96 L573.873 1720.96 L574.155 1720.96 L574.155 1720.96 L573.873 1720.96 L573.873 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="573.873,1720.96 573.873,1720.96 574.155,1720.96 573.873,1720.96 "/>
<path clip-path="url(#clip322)" d="M574.155 1720.96 L574.155 1720.96 L574.436 1720.96 L574.436 1720.96 L574.155 1720.96 L574.155 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="574.155,1720.96 574.155,1720.96 574.436,1720.96 574.155,1720.96 "/>
<path clip-path="url(#clip322)" d="M574.436 1720.96 L574.436 1720.96 L574.718 1720.96 L574.718 1720.96 L574.436 1720.96 L574.436 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="574.436,1720.96 574.436,1720.96 574.718,1720.96 574.436,1720.96 "/>
<path clip-path="url(#clip322)" d="M574.718 1720.96 L574.718 1720.96 L575 1720.96 L575 1720.96 L574.718 1720.96 L574.718 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="574.718,1720.96 574.718,1720.96 575,1720.96 574.718,1720.96 "/>
<path clip-path="url(#clip322)" d="M575 1720.96 L575 1720.96 L575.282 1720.96 L575.282 1720.96 L575 1720.96 L575 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="575,1720.96 575,1720.96 575.282,1720.96 575,1720.96 "/>
<path clip-path="url(#clip322)" d="M575.282 1720.96 L575.282 1720.96 L575.563 1720.96 L575.563 1720.96 L575.282 1720.96 L575.282 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="575.282,1720.96 575.282,1720.96 575.563,1720.96 575.282,1720.96 "/>
<path clip-path="url(#clip322)" d="M575.563 1720.96 L575.563 1720.96 L575.845 1720.96 L575.845 1720.96 L575.563 1720.96 L575.563 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="575.563,1720.96 575.563,1720.96 575.845,1720.96 575.563,1720.96 "/>
<path clip-path="url(#clip322)" d="M575.845 1720.96 L575.845 1720.96 L576.127 1720.96 L576.127 1720.96 L575.845 1720.96 L575.845 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="575.845,1720.96 575.845,1720.96 576.127,1720.96 575.845,1720.96 "/>
<path clip-path="url(#clip322)" d="M576.127 1720.96 L576.127 1720.96 L576.408 1720.96 L576.408 1720.96 L576.127 1720.96 L576.127 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="576.127,1720.96 576.127,1720.96 576.408,1720.96 576.127,1720.96 "/>
<path clip-path="url(#clip322)" d="M576.408 1720.96 L576.408 1720.96 L576.69 1720.96 L576.69 1720.96 L576.408 1720.96 L576.408 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="576.408,1720.96 576.408,1720.96 576.69,1720.96 576.408,1720.96 "/>
<path clip-path="url(#clip322)" d="M576.69 1720.96 L576.69 1720.96 L576.972 1720.96 L576.972 1720.96 L576.69 1720.96 L576.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="576.69,1720.96 576.69,1720.96 576.972,1720.96 576.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M576.972 1720.96 L576.972 1720.96 L577.254 1720.96 L577.254 1720.96 L576.972 1720.96 L576.972 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="576.972,1720.96 576.972,1720.96 577.254,1720.96 576.972,1720.96 "/>
<path clip-path="url(#clip322)" d="M577.254 1720.96 L577.254 1720.96 L577.535 1720.96 L577.535 1720.96 L577.254 1720.96 L577.254 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="577.254,1720.96 577.254,1720.96 577.535,1720.96 577.254,1720.96 "/>
<path clip-path="url(#clip322)" d="M577.535 1720.96 L577.535 1720.96 L577.817 1720.96 L577.817 1720.96 L577.535 1720.96 L577.535 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="577.535,1720.96 577.535,1720.96 577.817,1720.96 577.535,1720.96 "/>
<path clip-path="url(#clip322)" d="M577.817 1720.96 L577.817 1720.96 L578.099 1720.96 L578.099 1720.96 L577.817 1720.96 L577.817 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="577.817,1720.96 577.817,1720.96 578.099,1720.96 577.817,1720.96 "/>
<path clip-path="url(#clip322)" d="M578.099 1720.96 L578.099 1720.96 L578.38 1720.96 L578.38 1720.96 L578.099 1720.96 L578.099 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="578.099,1720.96 578.099,1720.96 578.38,1720.96 578.099,1720.96 "/>
<path clip-path="url(#clip322)" d="M578.38 1720.96 L578.38 1720.96 L578.662 1720.96 L578.662 1720.96 L578.38 1720.96 L578.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="578.38,1720.96 578.38,1720.96 578.662,1720.96 578.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M578.662 1720.96 L578.662 1720.96 L578.944 1720.96 L578.944 1720.96 L578.662 1720.96 L578.662 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="578.662,1720.96 578.662,1720.96 578.944,1720.96 578.662,1720.96 "/>
<path clip-path="url(#clip322)" d="M578.944 1720.96 L578.944 1720.96 L579.226 1720.96 L579.226 1720.96 L578.944 1720.96 L578.944 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="578.944,1720.96 578.944,1720.96 579.226,1720.96 578.944,1720.96 "/>
<path clip-path="url(#clip322)" d="M579.226 1720.96 L579.226 1720.96 L579.507 1720.96 L579.507 1720.96 L579.226 1720.96 L579.226 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="579.226,1720.96 579.226,1720.96 579.507,1720.96 579.226,1720.96 "/>
<path clip-path="url(#clip322)" d="M579.507 1720.96 L579.507 1720.96 L579.789 1720.96 L579.789 1720.96 L579.507 1720.96 L579.507 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="579.507,1720.96 579.507,1720.96 579.789,1720.96 579.507,1720.96 "/>
<path clip-path="url(#clip322)" d="M579.789 1720.96 L579.789 1720.96 L580.071 1720.96 L580.071 1720.96 L579.789 1720.96 L579.789 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="579.789,1720.96 579.789,1720.96 580.071,1720.96 579.789,1720.96 "/>
<path clip-path="url(#clip322)" d="M580.071 1720.96 L580.071 1720.96 L580.353 1720.96 L580.353 1720.96 L580.071 1720.96 L580.071 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="580.071,1720.96 580.071,1720.96 580.353,1720.96 580.071,1720.96 "/>
<path clip-path="url(#clip322)" d="M580.353 1720.96 L580.353 1720.96 L580.634 1720.96 L580.634 1720.96 L580.353 1720.96 L580.353 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="580.353,1720.96 580.353,1720.96 580.634,1720.96 580.353,1720.96 "/>
<path clip-path="url(#clip322)" d="M580.634 1720.96 L580.634 1720.96 L580.916 1720.96 L580.916 1720.96 L580.634 1720.96 L580.634 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="580.634,1720.96 580.634,1720.96 580.916,1720.96 580.634,1720.96 "/>
<path clip-path="url(#clip322)" d="M580.916 1720.96 L580.916 1720.96 L581.198 1720.96 L581.198 1720.96 L580.916 1720.96 L580.916 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="580.916,1720.96 580.916,1720.96 581.198,1720.96 580.916,1720.96 "/>
<path clip-path="url(#clip322)" d="M581.198 1720.96 L581.198 1720.96 L581.479 1720.96 L581.479 1720.96 L581.198 1720.96 L581.198 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="581.198,1720.96 581.198,1720.96 581.479,1720.96 581.198,1720.96 "/>
<path clip-path="url(#clip322)" d="M581.479 1720.96 L581.479 1720.96 L581.761 1720.96 L581.761 1720.96 L581.479 1720.96 L581.479 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="581.479,1720.96 581.479,1720.96 581.761,1720.96 581.479,1720.96 "/>
<path clip-path="url(#clip322)" d="M581.761 1720.96 L581.761 1720.96 L582.043 1720.96 L582.043 1720.96 L581.761 1720.96 L581.761 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="581.761,1720.96 581.761,1720.96 582.043,1720.96 581.761,1720.96 "/>
<path clip-path="url(#clip322)" d="M582.043 1720.96 L582.043 1720.96 L582.325 1720.96 L582.325 1720.96 L582.043 1720.96 L582.043 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="582.043,1720.96 582.043,1720.96 582.325,1720.96 582.043,1720.96 "/>
<path clip-path="url(#clip322)" d="M582.325 1720.96 L582.325 1720.96 L582.606 1720.96 L582.606 1720.96 L582.325 1720.96 L582.325 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="582.325,1720.96 582.325,1720.96 582.606,1720.96 582.325,1720.96 "/>
<path clip-path="url(#clip322)" d="M582.606 1720.96 L582.606 1720.96 L582.888 1720.96 L582.888 1720.96 L582.606 1720.96 L582.606 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="582.606,1720.96 582.606,1720.96 582.888,1720.96 582.606,1720.96 "/>
<path clip-path="url(#clip322)" d="M582.888 1720.96 L582.888 1720.96 L583.17 1720.96 L583.17 1720.96 L582.888 1720.96 L582.888 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="582.888,1720.96 582.888,1720.96 583.17,1720.96 582.888,1720.96 "/>
<path clip-path="url(#clip322)" d="M583.17 1720.96 L583.17 1720.96 L583.452 1720.96 L583.452 1720.96 L583.17 1720.96 L583.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="583.17,1720.96 583.17,1720.96 583.452,1720.96 583.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M583.452 1720.96 L583.452 1720.96 L583.733 1720.96 L583.733 1720.96 L583.452 1720.96 L583.452 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="583.452,1720.96 583.452,1720.96 583.733,1720.96 583.452,1720.96 "/>
<path clip-path="url(#clip322)" d="M583.733 1720.96 L583.733 1720.96 L584.015 1720.96 L584.015 1720.96 L583.733 1720.96 L583.733 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="583.733,1720.96 583.733,1720.96 584.015,1720.96 583.733,1720.96 "/>
<path clip-path="url(#clip322)" d="M584.015 1720.96 L584.015 1720.96 L584.297 1720.96 L584.297 1720.96 L584.015 1720.96 L584.015 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="584.015,1720.96 584.015,1720.96 584.297,1720.96 584.015,1720.96 "/>
<path clip-path="url(#clip322)" d="M584.297 1720.96 L584.297 1720.96 L584.578 1720.96 L584.578 1720.96 L584.297 1720.96 L584.297 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="584.297,1720.96 584.297,1720.96 584.578,1720.96 584.297,1720.96 "/>
<path clip-path="url(#clip322)" d="M584.578 1720.96 L584.578 1720.96 L584.86 1720.96 L584.86 1720.96 L584.578 1720.96 L584.578 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="584.578,1720.96 584.578,1720.96 584.86,1720.96 584.578,1720.96 "/>
<path clip-path="url(#clip322)" d="M584.86 1720.96 L584.86 1720.96 L585.142 1720.96 L585.142 1720.96 L584.86 1720.96 L584.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="584.86,1720.96 584.86,1720.96 585.142,1720.96 584.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M585.142 1720.96 L585.142 1720.96 L585.424 1720.96 L585.424 1720.96 L585.142 1720.96 L585.142 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="585.142,1720.96 585.142,1720.96 585.424,1720.96 585.142,1720.96 "/>
<path clip-path="url(#clip322)" d="M585.424 1720.96 L585.424 1720.96 L585.705 1720.96 L585.705 1720.96 L585.424 1720.96 L585.424 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="585.424,1720.96 585.424,1720.96 585.705,1720.96 585.424,1720.96 "/>
<path clip-path="url(#clip322)" d="M585.705 1720.96 L585.705 1720.96 L585.987 1720.96 L585.987 1720.96 L585.705 1720.96 L585.705 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="585.705,1720.96 585.705,1720.96 585.987,1720.96 585.705,1720.96 "/>
<path clip-path="url(#clip322)" d="M585.987 1720.96 L585.987 1720.96 L586.269 1720.96 L586.269 1720.96 L585.987 1720.96 L585.987 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="585.987,1720.96 585.987,1720.96 586.269,1720.96 585.987,1720.96 "/>
<path clip-path="url(#clip322)" d="M586.269 1720.96 L586.269 1720.96 L586.551 1720.96 L586.551 1720.96 L586.269 1720.96 L586.269 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="586.269,1720.96 586.269,1720.96 586.551,1720.96 586.269,1720.96 "/>
<path clip-path="url(#clip322)" d="M586.551 1720.96 L586.551 1720.96 L586.832 1720.96 L586.832 1720.96 L586.551 1720.96 L586.551 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="586.551,1720.96 586.551,1720.96 586.832,1720.96 586.551,1720.96 "/>
<path clip-path="url(#clip322)" d="M586.832 1720.96 L586.832 1720.96 L587.114 1720.96 L587.114 1720.96 L586.832 1720.96 L586.832 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="586.832,1720.96 586.832,1720.96 587.114,1720.96 586.832,1720.96 "/>
<path clip-path="url(#clip322)" d="M587.114 1720.96 L587.114 1720.96 L587.396 1720.96 L587.396 1720.96 L587.114 1720.96 L587.114 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="587.114,1720.96 587.114,1720.96 587.396,1720.96 587.114,1720.96 "/>
<path clip-path="url(#clip322)" d="M587.396 1720.96 L587.396 1720.96 L587.677 1720.96 L587.677 1720.96 L587.396 1720.96 L587.396 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="587.396,1720.96 587.396,1720.96 587.677,1720.96 587.396,1720.96 "/>
<path clip-path="url(#clip322)" d="M587.677 1720.96 L587.677 1720.96 L587.959 1720.96 L587.959 1720.96 L587.677 1720.96 L587.677 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="587.677,1720.96 587.677,1720.96 587.959,1720.96 587.677,1720.96 "/>
<path clip-path="url(#clip322)" d="M587.959 1720.96 L587.959 1720.96 L588.241 1720.96 L588.241 1720.96 L587.959 1720.96 L587.959 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="587.959,1720.96 587.959,1720.96 588.241,1720.96 587.959,1720.96 "/>
<path clip-path="url(#clip322)" d="M588.241 1720.96 L588.241 1720.96 L588.523 1720.96 L588.523 1720.96 L588.241 1720.96 L588.241 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="588.241,1720.96 588.241,1720.96 588.523,1720.96 588.241,1720.96 "/>
<path clip-path="url(#clip322)" d="M588.523 1720.96 L588.523 1720.96 L588.804 1720.96 L588.804 1720.96 L588.523 1720.96 L588.523 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="588.523,1720.96 588.523,1720.96 588.804,1720.96 588.523,1720.96 "/>
<path clip-path="url(#clip322)" d="M588.804 1720.96 L588.804 1720.96 L589.086 1720.96 L589.086 1720.96 L588.804 1720.96 L588.804 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="588.804,1720.96 588.804,1720.96 589.086,1720.96 588.804,1720.96 "/>
<path clip-path="url(#clip322)" d="M589.086 1720.96 L589.086 1720.96 L589.368 1720.96 L589.368 1720.96 L589.086 1720.96 L589.086 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="589.086,1720.96 589.086,1720.96 589.368,1720.96 589.086,1720.96 "/>
<path clip-path="url(#clip322)" d="M589.368 1720.96 L589.368 1720.96 L589.65 1720.96 L589.65 1720.96 L589.368 1720.96 L589.368 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="589.368,1720.96 589.368,1720.96 589.65,1720.96 589.368,1720.96 "/>
<path clip-path="url(#clip322)" d="M589.65 1720.96 L589.65 1720.96 L589.931 1720.96 L589.931 1720.96 L589.65 1720.96 L589.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="589.65,1720.96 589.65,1720.96 589.931,1720.96 589.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M589.931 1720.96 L589.931 1720.96 L590.213 1720.96 L590.213 1720.96 L589.931 1720.96 L589.931 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="589.931,1720.96 589.931,1720.96 590.213,1720.96 589.931,1720.96 "/>
<path clip-path="url(#clip322)" d="M590.213 1720.96 L590.213 1720.96 L590.495 1720.96 L590.495 1720.96 L590.213 1720.96 L590.213 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="590.213,1720.96 590.213,1720.96 590.495,1720.96 590.213,1720.96 "/>
<path clip-path="url(#clip322)" d="M590.495 1720.96 L590.495 1720.96 L590.776 1720.96 L590.776 1720.96 L590.495 1720.96 L590.495 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="590.495,1720.96 590.495,1720.96 590.776,1720.96 590.495,1720.96 "/>
<path clip-path="url(#clip322)" d="M590.776 1720.96 L590.776 1720.96 L591.058 1720.96 L591.058 1720.96 L590.776 1720.96 L590.776 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="590.776,1720.96 590.776,1720.96 591.058,1720.96 590.776,1720.96 "/>
<path clip-path="url(#clip322)" d="M591.058 1720.96 L591.058 1720.96 L591.34 1720.96 L591.34 1720.96 L591.058 1720.96 L591.058 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="591.058,1720.96 591.058,1720.96 591.34,1720.96 591.058,1720.96 "/>
<path clip-path="url(#clip322)" d="M591.34 1720.96 L591.34 1720.96 L591.622 1720.96 L591.622 1720.96 L591.34 1720.96 L591.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="591.34,1720.96 591.34,1720.96 591.622,1720.96 591.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M591.622 1720.96 L591.622 1720.96 L591.903 1720.96 L591.903 1720.96 L591.622 1720.96 L591.622 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="591.622,1720.96 591.622,1720.96 591.903,1720.96 591.622,1720.96 "/>
<path clip-path="url(#clip322)" d="M591.903 1720.96 L591.903 1720.96 L592.185 1720.96 L592.185 1720.96 L591.903 1720.96 L591.903 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="591.903,1720.96 591.903,1720.96 592.185,1720.96 591.903,1720.96 "/>
<path clip-path="url(#clip322)" d="M592.185 1720.96 L592.185 1720.96 L592.467 1720.96 L592.467 1720.96 L592.185 1720.96 L592.185 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="592.185,1720.96 592.185,1720.96 592.467,1720.96 592.185,1720.96 "/>
<path clip-path="url(#clip322)" d="M592.467 1720.96 L592.467 1720.96 L592.748 1720.96 L592.748 1720.96 L592.467 1720.96 L592.467 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="592.467,1720.96 592.467,1720.96 592.748,1720.96 592.467,1720.96 "/>
<path clip-path="url(#clip322)" d="M592.748 1720.96 L592.748 1720.96 L593.03 1720.96 L593.03 1720.96 L592.748 1720.96 L592.748 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="592.748,1720.96 592.748,1720.96 593.03,1720.96 592.748,1720.96 "/>
<path clip-path="url(#clip322)" d="M593.03 1720.96 L593.03 1720.96 L593.312 1720.96 L593.312 1720.96 L593.03 1720.96 L593.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="593.03,1720.96 593.03,1720.96 593.312,1720.96 593.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M593.312 1720.96 L593.312 1720.96 L593.594 1720.96 L593.594 1720.96 L593.312 1720.96 L593.312 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="593.312,1720.96 593.312,1720.96 593.594,1720.96 593.312,1720.96 "/>
<path clip-path="url(#clip322)" d="M593.594 1720.96 L593.594 1720.96 L593.875 1720.96 L593.875 1720.96 L593.594 1720.96 L593.594 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="593.594,1720.96 593.594,1720.96 593.875,1720.96 593.594,1720.96 "/>
<path clip-path="url(#clip322)" d="M593.875 1720.96 L593.875 1720.96 L594.157 1720.96 L594.157 1720.96 L593.875 1720.96 L593.875 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="593.875,1720.96 593.875,1720.96 594.157,1720.96 593.875,1720.96 "/>
<path clip-path="url(#clip322)" d="M594.157 1720.96 L594.157 1720.96 L594.439 1720.96 L594.439 1720.96 L594.157 1720.96 L594.157 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="594.157,1720.96 594.157,1720.96 594.439,1720.96 594.157,1720.96 "/>
<path clip-path="url(#clip322)" d="M594.439 1720.96 L594.439 1720.96 L594.721 1720.96 L594.721 1720.96 L594.439 1720.96 L594.439 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="594.439,1720.96 594.439,1720.96 594.721,1720.96 594.439,1720.96 "/>
<path clip-path="url(#clip322)" d="M594.721 1720.96 L594.721 1720.96 L595.002 1720.96 L595.002 1720.96 L594.721 1720.96 L594.721 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="594.721,1720.96 594.721,1720.96 595.002,1720.96 594.721,1720.96 "/>
<path clip-path="url(#clip322)" d="M595.002 1720.96 L595.002 1720.96 L595.284 1720.96 L595.284 1720.96 L595.002 1720.96 L595.002 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="595.002,1720.96 595.002,1720.96 595.284,1720.96 595.002,1720.96 "/>
<path clip-path="url(#clip322)" d="M595.284 1720.96 L595.284 1720.96 L595.566 1720.96 L595.566 1720.96 L595.284 1720.96 L595.284 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="595.284,1720.96 595.284,1720.96 595.566,1720.96 595.284,1720.96 "/>
<path clip-path="url(#clip322)" d="M595.566 1720.96 L595.566 1720.96 L595.847 1720.96 L595.847 1720.96 L595.566 1720.96 L595.566 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="595.566,1720.96 595.566,1720.96 595.847,1720.96 595.566,1720.96 "/>
<path clip-path="url(#clip322)" d="M595.847 1720.96 L595.847 1720.96 L596.129 1720.96 L596.129 1720.96 L595.847 1720.96 L595.847 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="595.847,1720.96 595.847,1720.96 596.129,1720.96 595.847,1720.96 "/>
<path clip-path="url(#clip322)" d="M596.129 1720.96 L596.129 1720.96 L596.411 1720.96 L596.411 1720.96 L596.129 1720.96 L596.129 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="596.129,1720.96 596.129,1720.96 596.411,1720.96 596.129,1720.96 "/>
<path clip-path="url(#clip322)" d="M596.411 1720.96 L596.411 1720.96 L596.693 1720.96 L596.693 1720.96 L596.411 1720.96 L596.411 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="596.411,1720.96 596.411,1720.96 596.693,1720.96 596.411,1720.96 "/>
<path clip-path="url(#clip322)" d="M596.693 1720.96 L596.693 1720.96 L596.974 1720.96 L596.974 1720.96 L596.693 1720.96 L596.693 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="596.693,1720.96 596.693,1720.96 596.974,1720.96 596.693,1720.96 "/>
<path clip-path="url(#clip322)" d="M596.974 1720.96 L596.974 1720.96 L597.256 1720.96 L597.256 1720.96 L596.974 1720.96 L596.974 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="596.974,1720.96 596.974,1720.96 597.256,1720.96 596.974,1720.96 "/>
<path clip-path="url(#clip322)" d="M597.256 1720.96 L597.256 1720.96 L597.538 1720.96 L597.538 1720.96 L597.256 1720.96 L597.256 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="597.256,1720.96 597.256,1720.96 597.538,1720.96 597.256,1720.96 "/>
<path clip-path="url(#clip322)" d="M597.538 1720.96 L597.538 1720.96 L597.82 1720.96 L597.82 1720.96 L597.538 1720.96 L597.538 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="597.538,1720.96 597.538,1720.96 597.82,1720.96 597.538,1720.96 "/>
<path clip-path="url(#clip322)" d="M597.82 1720.96 L597.82 1720.96 L598.101 1720.96 L598.101 1720.96 L597.82 1720.96 L597.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="597.82,1720.96 597.82,1720.96 598.101,1720.96 597.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M598.101 1720.96 L598.101 1720.96 L598.383 1720.96 L598.383 1720.96 L598.101 1720.96 L598.101 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="598.101,1720.96 598.101,1720.96 598.383,1720.96 598.101,1720.96 "/>
<path clip-path="url(#clip322)" d="M598.383 1720.96 L598.383 1720.96 L598.665 1720.96 L598.665 1720.96 L598.383 1720.96 L598.383 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="598.383,1720.96 598.383,1720.96 598.665,1720.96 598.383,1720.96 "/>
<path clip-path="url(#clip322)" d="M598.665 1720.96 L598.665 1720.96 L598.946 1720.96 L598.946 1720.96 L598.665 1720.96 L598.665 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="598.665,1720.96 598.665,1720.96 598.946,1720.96 598.665,1720.96 "/>
<path clip-path="url(#clip322)" d="M598.946 1720.96 L598.946 1720.96 L599.228 1720.96 L599.228 1720.96 L598.946 1720.96 L598.946 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="598.946,1720.96 598.946,1720.96 599.228,1720.96 598.946,1720.96 "/>
<path clip-path="url(#clip322)" d="M599.228 1720.96 L599.228 1720.96 L599.51 1720.96 L599.51 1720.96 L599.228 1720.96 L599.228 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="599.228,1720.96 599.228,1720.96 599.51,1720.96 599.228,1720.96 "/>
<path clip-path="url(#clip322)" d="M599.51 1720.96 L599.51 1720.96 L599.792 1720.96 L599.792 1720.96 L599.51 1720.96 L599.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="599.51,1720.96 599.51,1720.96 599.792,1720.96 599.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M599.792 1720.96 L599.792 1720.96 L600.073 1720.96 L600.073 1720.96 L599.792 1720.96 L599.792 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="599.792,1720.96 599.792,1720.96 600.073,1720.96 599.792,1720.96 "/>
<path clip-path="url(#clip322)" d="M600.073 1720.96 L600.073 1720.96 L600.355 1720.96 L600.355 1720.96 L600.073 1720.96 L600.073 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="600.073,1720.96 600.073,1720.96 600.355,1720.96 600.073,1720.96 "/>
<path clip-path="url(#clip322)" d="M600.355 1720.96 L600.355 1720.96 L600.637 1720.96 L600.637 1720.96 L600.355 1720.96 L600.355 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="600.355,1720.96 600.355,1720.96 600.637,1720.96 600.355,1720.96 "/>
<path clip-path="url(#clip322)" d="M600.637 1720.96 L600.637 1720.96 L600.919 1720.96 L600.919 1720.96 L600.637 1720.96 L600.637 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="600.637,1720.96 600.637,1720.96 600.919,1720.96 600.637,1720.96 "/>
<path clip-path="url(#clip322)" d="M600.919 1720.96 L600.919 1720.96 L601.2 1720.96 L601.2 1720.96 L600.919 1720.96 L600.919 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="600.919,1720.96 600.919,1720.96 601.2,1720.96 600.919,1720.96 "/>
<path clip-path="url(#clip322)" d="M601.2 1720.96 L601.2 1720.96 L601.482 1720.96 L601.482 1720.96 L601.2 1720.96 L601.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="601.2,1720.96 601.2,1720.96 601.482,1720.96 601.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M601.482 1720.96 L601.482 1720.96 L601.764 1720.96 L601.764 1720.96 L601.482 1720.96 L601.482 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="601.482,1720.96 601.482,1720.96 601.764,1720.96 601.482,1720.96 "/>
<path clip-path="url(#clip322)" d="M601.764 1720.96 L601.764 1720.96 L602.045 1720.96 L602.045 1720.96 L601.764 1720.96 L601.764 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="601.764,1720.96 601.764,1720.96 602.045,1720.96 601.764,1720.96 "/>
<path clip-path="url(#clip322)" d="M602.045 1720.96 L602.045 1720.96 L602.327 1720.96 L602.327 1720.96 L602.045 1720.96 L602.045 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="602.045,1720.96 602.045,1720.96 602.327,1720.96 602.045,1720.96 "/>
<path clip-path="url(#clip322)" d="M602.327 1720.96 L602.327 1720.96 L602.609 1720.96 L602.609 1720.96 L602.327 1720.96 L602.327 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="602.327,1720.96 602.327,1720.96 602.609,1720.96 602.327,1720.96 "/>
<path clip-path="url(#clip322)" d="M602.609 1720.96 L602.609 1720.96 L602.891 1720.96 L602.891 1720.96 L602.609 1720.96 L602.609 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="602.609,1720.96 602.609,1720.96 602.891,1720.96 602.609,1720.96 "/>
<path clip-path="url(#clip322)" d="M602.891 1720.96 L602.891 1720.96 L603.172 1720.96 L603.172 1720.96 L602.891 1720.96 L602.891 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="602.891,1720.96 602.891,1720.96 603.172,1720.96 602.891,1720.96 "/>
<path clip-path="url(#clip322)" d="M603.172 1720.96 L603.172 1720.96 L603.454 1720.96 L603.454 1720.96 L603.172 1720.96 L603.172 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="603.172,1720.96 603.172,1720.96 603.454,1720.96 603.172,1720.96 "/>
<path clip-path="url(#clip322)" d="M603.454 1720.96 L603.454 1720.96 L603.736 1720.96 L603.736 1720.96 L603.454 1720.96 L603.454 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="603.454,1720.96 603.454,1720.96 603.736,1720.96 603.454,1720.96 "/>
<path clip-path="url(#clip322)" d="M603.736 1720.96 L603.736 1720.96 L604.018 1720.96 L604.018 1720.96 L603.736 1720.96 L603.736 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="603.736,1720.96 603.736,1720.96 604.018,1720.96 603.736,1720.96 "/>
<path clip-path="url(#clip322)" d="M604.018 1720.96 L604.018 1720.96 L604.299 1720.96 L604.299 1720.96 L604.018 1720.96 L604.018 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="604.018,1720.96 604.018,1720.96 604.299,1720.96 604.018,1720.96 "/>
<path clip-path="url(#clip322)" d="M604.299 1720.96 L604.299 1720.96 L604.581 1720.96 L604.581 1720.96 L604.299 1720.96 L604.299 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="604.299,1720.96 604.299,1720.96 604.581,1720.96 604.299,1720.96 "/>
<path clip-path="url(#clip322)" d="M604.581 1720.96 L604.581 1720.96 L604.863 1720.96 L604.863 1720.96 L604.581 1720.96 L604.581 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="604.581,1720.96 604.581,1720.96 604.863,1720.96 604.581,1720.96 "/>
<path clip-path="url(#clip322)" d="M604.863 1720.96 L604.863 1720.96 L605.144 1720.96 L605.144 1720.96 L604.863 1720.96 L604.863 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="604.863,1720.96 604.863,1720.96 605.144,1720.96 604.863,1720.96 "/>
<path clip-path="url(#clip322)" d="M605.144 1720.96 L605.144 1720.96 L605.426 1720.96 L605.426 1720.96 L605.144 1720.96 L605.144 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="605.144,1720.96 605.144,1720.96 605.426,1720.96 605.144,1720.96 "/>
<path clip-path="url(#clip322)" d="M605.426 1720.96 L605.426 1720.96 L605.708 1720.96 L605.708 1720.96 L605.426 1720.96 L605.426 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="605.426,1720.96 605.426,1720.96 605.708,1720.96 605.426,1720.96 "/>
<path clip-path="url(#clip322)" d="M605.708 1720.96 L605.708 1720.96 L605.99 1720.96 L605.99 1720.96 L605.708 1720.96 L605.708 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="605.708,1720.96 605.708,1720.96 605.99,1720.96 605.708,1720.96 "/>
<path clip-path="url(#clip322)" d="M605.99 1720.96 L605.99 1720.96 L606.271 1720.96 L606.271 1720.96 L605.99 1720.96 L605.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="605.99,1720.96 605.99,1720.96 606.271,1720.96 605.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M606.271 1720.96 L606.271 1720.96 L606.553 1720.96 L606.553 1720.96 L606.271 1720.96 L606.271 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="606.271,1720.96 606.271,1720.96 606.553,1720.96 606.271,1720.96 "/>
<path clip-path="url(#clip322)" d="M606.553 1720.96 L606.553 1720.96 L606.835 1720.96 L606.835 1720.96 L606.553 1720.96 L606.553 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="606.553,1720.96 606.553,1720.96 606.835,1720.96 606.553,1720.96 "/>
<path clip-path="url(#clip322)" d="M606.835 1720.96 L606.835 1720.96 L607.116 1720.96 L607.116 1720.96 L606.835 1720.96 L606.835 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="606.835,1720.96 606.835,1720.96 607.116,1720.96 606.835,1720.96 "/>
<path clip-path="url(#clip322)" d="M607.116 1720.96 L607.116 1720.96 L607.398 1720.96 L607.398 1720.96 L607.116 1720.96 L607.116 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="607.116,1720.96 607.116,1720.96 607.398,1720.96 607.116,1720.96 "/>
<path clip-path="url(#clip322)" d="M607.398 1720.96 L607.398 1720.96 L607.68 1720.96 L607.68 1720.96 L607.398 1720.96 L607.398 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="607.398,1720.96 607.398,1720.96 607.68,1720.96 607.398,1720.96 "/>
<path clip-path="url(#clip322)" d="M607.68 1720.96 L607.68 1720.96 L607.962 1720.96 L607.962 1720.96 L607.68 1720.96 L607.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="607.68,1720.96 607.68,1720.96 607.962,1720.96 607.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M607.962 1720.96 L607.962 1720.96 L608.243 1720.96 L608.243 1720.96 L607.962 1720.96 L607.962 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="607.962,1720.96 607.962,1720.96 608.243,1720.96 607.962,1720.96 "/>
<path clip-path="url(#clip322)" d="M608.243 1720.96 L608.243 1720.96 L608.525 1720.96 L608.525 1720.96 L608.243 1720.96 L608.243 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="608.243,1720.96 608.243,1720.96 608.525,1720.96 608.243,1720.96 "/>
<path clip-path="url(#clip322)" d="M608.525 1720.96 L608.525 1720.96 L608.807 1720.96 L608.807 1720.96 L608.525 1720.96 L608.525 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="608.525,1720.96 608.525,1720.96 608.807,1720.96 608.525,1720.96 "/>
<path clip-path="url(#clip322)" d="M608.807 1720.96 L608.807 1720.96 L609.089 1720.96 L609.089 1720.96 L608.807 1720.96 L608.807 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="608.807,1720.96 608.807,1720.96 609.089,1720.96 608.807,1720.96 "/>
<path clip-path="url(#clip322)" d="M609.089 1720.96 L609.089 1720.96 L609.37 1720.96 L609.37 1720.96 L609.089 1720.96 L609.089 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="609.089,1720.96 609.089,1720.96 609.37,1720.96 609.089,1720.96 "/>
<path clip-path="url(#clip322)" d="M609.37 1720.96 L609.37 1720.96 L609.652 1720.96 L609.652 1720.96 L609.37 1720.96 L609.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="609.37,1720.96 609.37,1720.96 609.652,1720.96 609.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M609.652 1720.96 L609.652 1720.96 L609.934 1720.96 L609.934 1720.96 L609.652 1720.96 L609.652 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="609.652,1720.96 609.652,1720.96 609.934,1720.96 609.652,1720.96 "/>
<path clip-path="url(#clip322)" d="M609.934 1720.96 L609.934 1720.96 L610.215 1720.96 L610.215 1720.96 L609.934 1720.96 L609.934 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="609.934,1720.96 609.934,1720.96 610.215,1720.96 609.934,1720.96 "/>
<path clip-path="url(#clip322)" d="M610.215 1720.96 L610.215 1720.96 L610.497 1720.96 L610.497 1720.96 L610.215 1720.96 L610.215 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="610.215,1720.96 610.215,1720.96 610.497,1720.96 610.215,1720.96 "/>
<path clip-path="url(#clip322)" d="M610.497 1720.96 L610.497 1720.96 L610.779 1720.96 L610.779 1720.96 L610.497 1720.96 L610.497 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="610.497,1720.96 610.497,1720.96 610.779,1720.96 610.497,1720.96 "/>
<path clip-path="url(#clip322)" d="M610.779 1720.96 L610.779 1720.96 L611.061 1720.96 L611.061 1720.96 L610.779 1720.96 L610.779 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="610.779,1720.96 610.779,1720.96 611.061,1720.96 610.779,1720.96 "/>
<path clip-path="url(#clip322)" d="M611.061 1720.96 L611.061 1720.96 L611.342 1720.96 L611.342 1720.96 L611.061 1720.96 L611.061 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="611.061,1720.96 611.061,1720.96 611.342,1720.96 611.061,1720.96 "/>
<path clip-path="url(#clip322)" d="M611.342 1720.96 L611.342 1720.96 L611.624 1720.96 L611.624 1720.96 L611.342 1720.96 L611.342 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="611.342,1720.96 611.342,1720.96 611.624,1720.96 611.342,1720.96 "/>
<path clip-path="url(#clip322)" d="M611.624 1720.96 L611.624 1720.96 L611.906 1720.96 L611.906 1720.96 L611.624 1720.96 L611.624 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="611.624,1720.96 611.624,1720.96 611.906,1720.96 611.624,1720.96 "/>
<path clip-path="url(#clip322)" d="M611.906 1720.96 L611.906 1720.96 L612.188 1720.96 L612.188 1720.96 L611.906 1720.96 L611.906 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="611.906,1720.96 611.906,1720.96 612.188,1720.96 611.906,1720.96 "/>
<path clip-path="url(#clip322)" d="M612.188 1720.96 L612.188 1720.96 L612.469 1720.96 L612.469 1720.96 L612.188 1720.96 L612.188 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="612.188,1720.96 612.188,1720.96 612.469,1720.96 612.188,1720.96 "/>
<path clip-path="url(#clip322)" d="M612.469 1720.96 L612.469 1720.96 L612.751 1720.96 L612.751 1720.96 L612.469 1720.96 L612.469 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="612.469,1720.96 612.469,1720.96 612.751,1720.96 612.469,1720.96 "/>
<path clip-path="url(#clip322)" d="M612.751 1720.96 L612.751 1720.96 L613.033 1720.96 L613.033 1720.96 L612.751 1720.96 L612.751 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="612.751,1720.96 612.751,1720.96 613.033,1720.96 612.751,1720.96 "/>
<path clip-path="url(#clip322)" d="M613.033 1720.96 L613.033 1720.96 L613.314 1720.96 L613.314 1720.96 L613.033 1720.96 L613.033 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="613.033,1720.96 613.033,1720.96 613.314,1720.96 613.033,1720.96 "/>
<path clip-path="url(#clip322)" d="M613.314 1720.96 L613.314 1720.96 L613.596 1720.96 L613.596 1720.96 L613.314 1720.96 L613.314 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="613.314,1720.96 613.314,1720.96 613.596,1720.96 613.314,1720.96 "/>
<path clip-path="url(#clip322)" d="M613.596 1720.96 L613.596 1720.96 L613.878 1720.96 L613.878 1720.96 L613.596 1720.96 L613.596 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="613.596,1720.96 613.596,1720.96 613.878,1720.96 613.596,1720.96 "/>
<path clip-path="url(#clip322)" d="M613.878 1720.96 L613.878 1720.96 L614.16 1720.96 L614.16 1720.96 L613.878 1720.96 L613.878 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="613.878,1720.96 613.878,1720.96 614.16,1720.96 613.878,1720.96 "/>
<path clip-path="url(#clip322)" d="M614.16 1720.96 L614.16 1720.96 L614.441 1720.96 L614.441 1720.96 L614.16 1720.96 L614.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="614.16,1720.96 614.16,1720.96 614.441,1720.96 614.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M614.441 1720.96 L614.441 1720.96 L614.723 1720.96 L614.723 1720.96 L614.441 1720.96 L614.441 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="614.441,1720.96 614.441,1720.96 614.723,1720.96 614.441,1720.96 "/>
<path clip-path="url(#clip322)" d="M614.723 1720.96 L614.723 1720.96 L615.005 1720.96 L615.005 1720.96 L614.723 1720.96 L614.723 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="614.723,1720.96 614.723,1720.96 615.005,1720.96 614.723,1720.96 "/>
<path clip-path="url(#clip322)" d="M615.005 1720.96 L615.005 1720.96 L615.287 1720.96 L615.287 1720.96 L615.005 1720.96 L615.005 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="615.005,1720.96 615.005,1720.96 615.287,1720.96 615.005,1720.96 "/>
<path clip-path="url(#clip322)" d="M615.287 1720.96 L615.287 1720.96 L615.568 1720.96 L615.568 1720.96 L615.287 1720.96 L615.287 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="615.287,1720.96 615.287,1720.96 615.568,1720.96 615.287,1720.96 "/>
<path clip-path="url(#clip322)" d="M615.568 1720.96 L615.568 1720.96 L615.85 1720.96 L615.85 1720.96 L615.568 1720.96 L615.568 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="615.568,1720.96 615.568,1720.96 615.85,1720.96 615.568,1720.96 "/>
<path clip-path="url(#clip322)" d="M615.85 1720.96 L615.85 1720.96 L616.132 1720.96 L616.132 1720.96 L615.85 1720.96 L615.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="615.85,1720.96 615.85,1720.96 616.132,1720.96 615.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M616.132 1720.96 L616.132 1720.96 L616.413 1720.96 L616.413 1720.96 L616.132 1720.96 L616.132 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="616.132,1720.96 616.132,1720.96 616.413,1720.96 616.132,1720.96 "/>
<path clip-path="url(#clip322)" d="M616.413 1720.96 L616.413 1720.96 L616.695 1720.96 L616.695 1720.96 L616.413 1720.96 L616.413 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="616.413,1720.96 616.413,1720.96 616.695,1720.96 616.413,1720.96 "/>
<path clip-path="url(#clip322)" d="M616.695 1720.96 L616.695 1720.96 L616.977 1720.96 L616.977 1720.96 L616.695 1720.96 L616.695 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="616.695,1720.96 616.695,1720.96 616.977,1720.96 616.695,1720.96 "/>
<path clip-path="url(#clip322)" d="M616.977 1720.96 L616.977 1720.96 L617.259 1720.96 L617.259 1720.96 L616.977 1720.96 L616.977 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="616.977,1720.96 616.977,1720.96 617.259,1720.96 616.977,1720.96 "/>
<path clip-path="url(#clip322)" d="M617.259 1720.96 L617.259 1720.96 L617.54 1720.96 L617.54 1720.96 L617.259 1720.96 L617.259 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="617.259,1720.96 617.259,1720.96 617.54,1720.96 617.259,1720.96 "/>
<path clip-path="url(#clip322)" d="M617.54 1720.96 L617.54 1720.96 L617.822 1720.96 L617.822 1720.96 L617.54 1720.96 L617.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="617.54,1720.96 617.54,1720.96 617.822,1720.96 617.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M617.822 1720.96 L617.822 1720.96 L618.104 1720.96 L618.104 1720.96 L617.822 1720.96 L617.822 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="617.822,1720.96 617.822,1720.96 618.104,1720.96 617.822,1720.96 "/>
<path clip-path="url(#clip322)" d="M618.104 1720.96 L618.104 1720.96 L618.386 1720.96 L618.386 1720.96 L618.104 1720.96 L618.104 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="618.104,1720.96 618.104,1720.96 618.386,1720.96 618.104,1720.96 "/>
<path clip-path="url(#clip322)" d="M618.386 1720.96 L618.386 1720.96 L618.667 1720.96 L618.667 1720.96 L618.386 1720.96 L618.386 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="618.386,1720.96 618.386,1720.96 618.667,1720.96 618.386,1720.96 "/>
<path clip-path="url(#clip322)" d="M618.667 1720.96 L618.667 1720.96 L618.949 1720.96 L618.949 1720.96 L618.667 1720.96 L618.667 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="618.667,1720.96 618.667,1720.96 618.949,1720.96 618.667,1720.96 "/>
<path clip-path="url(#clip322)" d="M618.949 1720.96 L618.949 1720.96 L619.231 1720.96 L619.231 1720.96 L618.949 1720.96 L618.949 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="618.949,1720.96 618.949,1720.96 619.231,1720.96 618.949,1720.96 "/>
<path clip-path="url(#clip322)" d="M619.231 1720.96 L619.231 1720.96 L619.512 1720.96 L619.512 1720.96 L619.231 1720.96 L619.231 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="619.231,1720.96 619.231,1720.96 619.512,1720.96 619.231,1720.96 "/>
<path clip-path="url(#clip322)" d="M619.512 1720.96 L619.512 1720.96 L619.794 1720.96 L619.794 1720.96 L619.512 1720.96 L619.512 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="619.512,1720.96 619.512,1720.96 619.794,1720.96 619.512,1720.96 "/>
<path clip-path="url(#clip322)" d="M619.794 1720.96 L619.794 1720.96 L620.076 1720.96 L620.076 1720.96 L619.794 1720.96 L619.794 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="619.794,1720.96 619.794,1720.96 620.076,1720.96 619.794,1720.96 "/>
<path clip-path="url(#clip322)" d="M620.076 1720.96 L620.076 1720.96 L620.358 1720.96 L620.358 1720.96 L620.076 1720.96 L620.076 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="620.076,1720.96 620.076,1720.96 620.358,1720.96 620.076,1720.96 "/>
<path clip-path="url(#clip322)" d="M620.358 1720.96 L620.358 1720.96 L620.639 1720.96 L620.639 1720.96 L620.358 1720.96 L620.358 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="620.358,1720.96 620.358,1720.96 620.639,1720.96 620.358,1720.96 "/>
<path clip-path="url(#clip322)" d="M620.639 1720.96 L620.639 1720.96 L620.921 1720.96 L620.921 1720.96 L620.639 1720.96 L620.639 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="620.639,1720.96 620.639,1720.96 620.921,1720.96 620.639,1720.96 "/>
<path clip-path="url(#clip322)" d="M620.921 1720.96 L620.921 1720.96 L621.203 1720.96 L621.203 1720.96 L620.921 1720.96 L620.921 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="620.921,1720.96 620.921,1720.96 621.203,1720.96 620.921,1720.96 "/>
<path clip-path="url(#clip322)" d="M621.203 1720.96 L621.203 1720.96 L621.485 1720.96 L621.485 1720.96 L621.203 1720.96 L621.203 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="621.203,1720.96 621.203,1720.96 621.485,1720.96 621.203,1720.96 "/>
<path clip-path="url(#clip322)" d="M621.485 1720.96 L621.485 1720.96 L621.766 1720.96 L621.766 1720.96 L621.485 1720.96 L621.485 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="621.485,1720.96 621.485,1720.96 621.766,1720.96 621.485,1720.96 "/>
<path clip-path="url(#clip322)" d="M621.766 1720.96 L621.766 1720.96 L622.048 1720.96 L622.048 1720.96 L621.766 1720.96 L621.766 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="621.766,1720.96 621.766,1720.96 622.048,1720.96 621.766,1720.96 "/>
<path clip-path="url(#clip322)" d="M622.048 1720.96 L622.048 1720.96 L622.33 1720.96 L622.33 1720.96 L622.048 1720.96 L622.048 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="622.048,1720.96 622.048,1720.96 622.33,1720.96 622.048,1720.96 "/>
<path clip-path="url(#clip322)" d="M622.33 1720.96 L622.33 1720.96 L622.611 1720.96 L622.611 1720.96 L622.33 1720.96 L622.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="622.33,1720.96 622.33,1720.96 622.611,1720.96 622.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M622.611 1720.96 L622.611 1720.96 L622.893 1720.96 L622.893 1720.96 L622.611 1720.96 L622.611 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="622.611,1720.96 622.611,1720.96 622.893,1720.96 622.611,1720.96 "/>
<path clip-path="url(#clip322)" d="M622.893 1720.96 L622.893 1720.96 L623.175 1720.96 L623.175 1720.96 L622.893 1720.96 L622.893 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="622.893,1720.96 622.893,1720.96 623.175,1720.96 622.893,1720.96 "/>
<path clip-path="url(#clip322)" d="M623.175 1720.96 L623.175 1720.96 L623.457 1720.96 L623.457 1720.96 L623.175 1720.96 L623.175 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="623.175,1720.96 623.175,1720.96 623.457,1720.96 623.175,1720.96 "/>
<path clip-path="url(#clip322)" d="M623.457 1720.96 L623.457 1720.96 L623.738 1720.96 L623.738 1720.96 L623.457 1720.96 L623.457 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="623.457,1720.96 623.457,1720.96 623.738,1720.96 623.457,1720.96 "/>
<path clip-path="url(#clip322)" d="M623.738 1720.96 L623.738 1720.96 L624.02 1720.96 L624.02 1720.96 L623.738 1720.96 L623.738 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="623.738,1720.96 623.738,1720.96 624.02,1720.96 623.738,1720.96 "/>
<path clip-path="url(#clip322)" d="M624.02 1720.96 L624.02 1720.96 L624.302 1720.96 L624.302 1720.96 L624.02 1720.96 L624.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="624.02,1720.96 624.02,1720.96 624.302,1720.96 624.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M624.302 1720.96 L624.302 1720.96 L624.583 1720.96 L624.583 1720.96 L624.302 1720.96 L624.302 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="624.302,1720.96 624.302,1720.96 624.583,1720.96 624.302,1720.96 "/>
<path clip-path="url(#clip322)" d="M624.583 1720.96 L624.583 1720.96 L624.865 1720.96 L624.865 1720.96 L624.583 1720.96 L624.583 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="624.583,1720.96 624.583,1720.96 624.865,1720.96 624.583,1720.96 "/>
<path clip-path="url(#clip322)" d="M624.865 1720.96 L624.865 1720.96 L625.147 1720.96 L625.147 1720.96 L624.865 1720.96 L624.865 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="624.865,1720.96 624.865,1720.96 625.147,1720.96 624.865,1720.96 "/>
<path clip-path="url(#clip322)" d="M625.147 1720.96 L625.147 1720.96 L625.429 1720.96 L625.429 1720.96 L625.147 1720.96 L625.147 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="625.147,1720.96 625.147,1720.96 625.429,1720.96 625.147,1720.96 "/>
<path clip-path="url(#clip322)" d="M625.429 1720.96 L625.429 1720.96 L625.71 1720.96 L625.71 1720.96 L625.429 1720.96 L625.429 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="625.429,1720.96 625.429,1720.96 625.71,1720.96 625.429,1720.96 "/>
<path clip-path="url(#clip322)" d="M625.71 1720.96 L625.71 1720.96 L625.992 1720.96 L625.992 1720.96 L625.71 1720.96 L625.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="625.71,1720.96 625.71,1720.96 625.992,1720.96 625.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M625.992 1720.96 L625.992 1720.96 L626.274 1720.96 L626.274 1720.96 L625.992 1720.96 L625.992 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="625.992,1720.96 625.992,1720.96 626.274,1720.96 625.992,1720.96 "/>
<path clip-path="url(#clip322)" d="M626.274 1720.96 L626.274 1720.96 L626.556 1720.96 L626.556 1720.96 L626.274 1720.96 L626.274 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="626.274,1720.96 626.274,1720.96 626.556,1720.96 626.274,1720.96 "/>
<path clip-path="url(#clip322)" d="M626.556 1720.96 L626.556 1720.96 L626.837 1720.96 L626.837 1720.96 L626.556 1720.96 L626.556 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="626.556,1720.96 626.556,1720.96 626.837,1720.96 626.556,1720.96 "/>
<path clip-path="url(#clip322)" d="M626.837 1720.96 L626.837 1720.96 L627.119 1720.96 L627.119 1720.96 L626.837 1720.96 L626.837 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="626.837,1720.96 626.837,1720.96 627.119,1720.96 626.837,1720.96 "/>
<path clip-path="url(#clip322)" d="M627.119 1720.96 L627.119 1720.96 L627.401 1720.96 L627.401 1720.96 L627.119 1720.96 L627.119 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="627.119,1720.96 627.119,1720.96 627.401,1720.96 627.119,1720.96 "/>
<path clip-path="url(#clip322)" d="M627.401 1720.96 L627.401 1720.96 L627.682 1720.96 L627.682 1720.96 L627.401 1720.96 L627.401 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="627.401,1720.96 627.401,1720.96 627.682,1720.96 627.401,1720.96 "/>
<path clip-path="url(#clip322)" d="M627.682 1720.96 L627.682 1720.96 L627.964 1720.96 L627.964 1720.96 L627.682 1720.96 L627.682 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="627.682,1720.96 627.682,1720.96 627.964,1720.96 627.682,1720.96 "/>
<path clip-path="url(#clip322)" d="M627.964 1720.96 L627.964 1720.96 L628.246 1720.96 L628.246 1720.96 L627.964 1720.96 L627.964 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="627.964,1720.96 627.964,1720.96 628.246,1720.96 627.964,1720.96 "/>
<path clip-path="url(#clip322)" d="M628.246 1720.96 L628.246 1720.96 L628.528 1720.96 L628.528 1720.96 L628.246 1720.96 L628.246 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="628.246,1720.96 628.246,1720.96 628.528,1720.96 628.246,1720.96 "/>
<path clip-path="url(#clip322)" d="M628.528 1720.96 L628.528 1720.96 L628.809 1720.96 L628.809 1720.96 L628.528 1720.96 L628.528 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="628.528,1720.96 628.528,1720.96 628.809,1720.96 628.528,1720.96 "/>
<path clip-path="url(#clip322)" d="M628.809 1720.96 L628.809 1720.96 L629.091 1720.96 L629.091 1720.96 L628.809 1720.96 L628.809 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="628.809,1720.96 628.809,1720.96 629.091,1720.96 628.809,1720.96 "/>
<path clip-path="url(#clip322)" d="M629.091 1720.96 L629.091 1720.96 L629.373 1720.96 L629.373 1720.96 L629.091 1720.96 L629.091 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="629.091,1720.96 629.091,1720.96 629.373,1720.96 629.091,1720.96 "/>
<path clip-path="url(#clip322)" d="M629.373 1720.96 L629.373 1720.96 L629.655 1720.96 L629.655 1720.96 L629.373 1720.96 L629.373 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="629.373,1720.96 629.373,1720.96 629.655,1720.96 629.373,1720.96 "/>
<path clip-path="url(#clip322)" d="M629.655 1720.96 L629.655 1720.96 L629.936 1720.96 L629.936 1720.96 L629.655 1720.96 L629.655 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="629.655,1720.96 629.655,1720.96 629.936,1720.96 629.655,1720.96 "/>
<path clip-path="url(#clip322)" d="M629.936 1720.96 L629.936 1720.96 L630.218 1720.96 L630.218 1720.96 L629.936 1720.96 L629.936 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="629.936,1720.96 629.936,1720.96 630.218,1720.96 629.936,1720.96 "/>
<path clip-path="url(#clip322)" d="M630.218 1720.96 L630.218 1720.96 L630.5 1720.96 L630.5 1720.96 L630.218 1720.96 L630.218 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="630.218,1720.96 630.218,1720.96 630.5,1720.96 630.218,1720.96 "/>
<path clip-path="url(#clip322)" d="M630.5 1720.96 L630.5 1720.96 L630.781 1720.96 L630.781 1720.96 L630.5 1720.96 L630.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="630.5,1720.96 630.5,1720.96 630.781,1720.96 630.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M630.781 1720.96 L630.781 1720.96 L631.063 1720.96 L631.063 1720.96 L630.781 1720.96 L630.781 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="630.781,1720.96 630.781,1720.96 631.063,1720.96 630.781,1720.96 "/>
<path clip-path="url(#clip322)" d="M631.063 1720.96 L631.063 1720.96 L631.345 1720.96 L631.345 1720.96 L631.063 1720.96 L631.063 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="631.063,1720.96 631.063,1720.96 631.345,1720.96 631.063,1720.96 "/>
<path clip-path="url(#clip322)" d="M631.345 1720.96 L631.345 1720.96 L631.627 1720.96 L631.627 1720.96 L631.345 1720.96 L631.345 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="631.345,1720.96 631.345,1720.96 631.627,1720.96 631.345,1720.96 "/>
<path clip-path="url(#clip322)" d="M631.627 1720.96 L631.627 1720.96 L631.908 1720.96 L631.908 1720.96 L631.627 1720.96 L631.627 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="631.627,1720.96 631.627,1720.96 631.908,1720.96 631.627,1720.96 "/>
<path clip-path="url(#clip322)" d="M631.908 1720.96 L631.908 1720.96 L632.19 1720.96 L632.19 1720.96 L631.908 1720.96 L631.908 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="631.908,1720.96 631.908,1720.96 632.19,1720.96 631.908,1720.96 "/>
<path clip-path="url(#clip322)" d="M632.19 1720.96 L632.19 1720.96 L632.472 1720.96 L632.472 1720.96 L632.19 1720.96 L632.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="632.19,1720.96 632.19,1720.96 632.472,1720.96 632.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M632.472 1720.96 L632.472 1720.96 L632.754 1720.96 L632.754 1720.96 L632.472 1720.96 L632.472 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="632.472,1720.96 632.472,1720.96 632.754,1720.96 632.472,1720.96 "/>
<path clip-path="url(#clip322)" d="M632.754 1720.96 L632.754 1720.96 L633.035 1720.96 L633.035 1720.96 L632.754 1720.96 L632.754 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="632.754,1720.96 632.754,1720.96 633.035,1720.96 632.754,1720.96 "/>
<path clip-path="url(#clip322)" d="M633.035 1720.96 L633.035 1720.96 L633.317 1720.96 L633.317 1720.96 L633.035 1720.96 L633.035 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="633.035,1720.96 633.035,1720.96 633.317,1720.96 633.035,1720.96 "/>
<path clip-path="url(#clip322)" d="M633.317 1720.96 L633.317 1720.96 L633.599 1720.96 L633.599 1720.96 L633.317 1720.96 L633.317 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="633.317,1720.96 633.317,1720.96 633.599,1720.96 633.317,1720.96 "/>
<path clip-path="url(#clip322)" d="M633.599 1720.96 L633.599 1720.96 L633.88 1720.96 L633.88 1720.96 L633.599 1720.96 L633.599 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="633.599,1720.96 633.599,1720.96 633.88,1720.96 633.599,1720.96 "/>
<path clip-path="url(#clip322)" d="M633.88 1720.96 L633.88 1720.96 L634.162 1720.96 L634.162 1720.96 L633.88 1720.96 L633.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="633.88,1720.96 633.88,1720.96 634.162,1720.96 633.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M634.162 1720.96 L634.162 1720.96 L634.444 1720.96 L634.444 1720.96 L634.162 1720.96 L634.162 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="634.162,1720.96 634.162,1720.96 634.444,1720.96 634.162,1720.96 "/>
<path clip-path="url(#clip322)" d="M634.444 1720.96 L634.444 1720.96 L634.726 1720.96 L634.726 1720.96 L634.444 1720.96 L634.444 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="634.444,1720.96 634.444,1720.96 634.726,1720.96 634.444,1720.96 "/>
<path clip-path="url(#clip322)" d="M634.726 1720.96 L634.726 1720.96 L635.007 1720.96 L635.007 1720.96 L634.726 1720.96 L634.726 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="634.726,1720.96 634.726,1720.96 635.007,1720.96 634.726,1720.96 "/>
<path clip-path="url(#clip322)" d="M635.007 1720.96 L635.007 1720.96 L635.289 1720.96 L635.289 1720.96 L635.007 1720.96 L635.007 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="635.007,1720.96 635.007,1720.96 635.289,1720.96 635.007,1720.96 "/>
<path clip-path="url(#clip322)" d="M635.289 1720.96 L635.289 1720.96 L635.571 1720.96 L635.571 1720.96 L635.289 1720.96 L635.289 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="635.289,1720.96 635.289,1720.96 635.571,1720.96 635.289,1720.96 "/>
<path clip-path="url(#clip322)" d="M635.571 1720.96 L635.571 1720.96 L635.853 1720.96 L635.853 1720.96 L635.571 1720.96 L635.571 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="635.571,1720.96 635.571,1720.96 635.853,1720.96 635.571,1720.96 "/>
<path clip-path="url(#clip322)" d="M635.853 1720.96 L635.853 1720.96 L636.134 1720.96 L636.134 1720.96 L635.853 1720.96 L635.853 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="635.853,1720.96 635.853,1720.96 636.134,1720.96 635.853,1720.96 "/>
<path clip-path="url(#clip322)" d="M636.134 1720.96 L636.134 1720.96 L636.416 1720.96 L636.416 1720.96 L636.134 1720.96 L636.134 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="636.134,1720.96 636.134,1720.96 636.416,1720.96 636.134,1720.96 "/>
<path clip-path="url(#clip322)" d="M636.416 1720.96 L636.416 1720.96 L636.698 1720.96 L636.698 1720.96 L636.416 1720.96 L636.416 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="636.416,1720.96 636.416,1720.96 636.698,1720.96 636.416,1720.96 "/>
<path clip-path="url(#clip322)" d="M636.698 1720.96 L636.698 1720.96 L636.979 1720.96 L636.979 1720.96 L636.698 1720.96 L636.698 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="636.698,1720.96 636.698,1720.96 636.979,1720.96 636.698,1720.96 "/>
<path clip-path="url(#clip322)" d="M636.979 1720.96 L636.979 1720.96 L637.261 1720.96 L637.261 1720.96 L636.979 1720.96 L636.979 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="636.979,1720.96 636.979,1720.96 637.261,1720.96 636.979,1720.96 "/>
<path clip-path="url(#clip322)" d="M637.261 1720.96 L637.261 1720.96 L637.543 1720.96 L637.543 1720.96 L637.261 1720.96 L637.261 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="637.261,1720.96 637.261,1720.96 637.543,1720.96 637.261,1720.96 "/>
<path clip-path="url(#clip322)" d="M637.543 1720.96 L637.543 1720.96 L637.825 1720.96 L637.825 1720.96 L637.543 1720.96 L637.543 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="637.543,1720.96 637.543,1720.96 637.825,1720.96 637.543,1720.96 "/>
<path clip-path="url(#clip322)" d="M637.825 1720.96 L637.825 1720.96 L638.106 1720.96 L638.106 1720.96 L637.825 1720.96 L637.825 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="637.825,1720.96 637.825,1720.96 638.106,1720.96 637.825,1720.96 "/>
<path clip-path="url(#clip322)" d="M638.106 1720.96 L638.106 1720.96 L638.388 1720.96 L638.388 1720.96 L638.106 1720.96 L638.106 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="638.106,1720.96 638.106,1720.96 638.388,1720.96 638.106,1720.96 "/>
<path clip-path="url(#clip322)" d="M638.388 1720.96 L638.388 1720.96 L638.67 1720.96 L638.67 1720.96 L638.388 1720.96 L638.388 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="638.388,1720.96 638.388,1720.96 638.67,1720.96 638.388,1720.96 "/>
<path clip-path="url(#clip322)" d="M638.67 1720.96 L638.67 1720.96 L638.951 1720.96 L638.951 1720.96 L638.67 1720.96 L638.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="638.67,1720.96 638.67,1720.96 638.951,1720.96 638.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M638.951 1720.96 L638.951 1720.96 L639.233 1720.96 L639.233 1720.96 L638.951 1720.96 L638.951 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="638.951,1720.96 638.951,1720.96 639.233,1720.96 638.951,1720.96 "/>
<path clip-path="url(#clip322)" d="M639.233 1720.96 L639.233 1720.96 L639.515 1720.96 L639.515 1720.96 L639.233 1720.96 L639.233 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="639.233,1720.96 639.233,1720.96 639.515,1720.96 639.233,1720.96 "/>
<path clip-path="url(#clip322)" d="M639.515 1720.96 L639.515 1720.96 L639.797 1720.96 L639.797 1720.96 L639.515 1720.96 L639.515 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="639.515,1720.96 639.515,1720.96 639.797,1720.96 639.515,1720.96 "/>
<path clip-path="url(#clip322)" d="M639.797 1720.96 L639.797 1720.96 L640.078 1720.96 L640.078 1720.96 L639.797 1720.96 L639.797 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="639.797,1720.96 639.797,1720.96 640.078,1720.96 639.797,1720.96 "/>
<path clip-path="url(#clip322)" d="M640.078 1720.96 L640.078 1720.96 L640.36 1720.96 L640.36 1720.96 L640.078 1720.96 L640.078 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="640.078,1720.96 640.078,1720.96 640.36,1720.96 640.078,1720.96 "/>
<path clip-path="url(#clip322)" d="M640.36 1720.96 L640.36 1720.96 L640.642 1720.96 L640.642 1720.96 L640.36 1720.96 L640.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="640.36,1720.96 640.36,1720.96 640.642,1720.96 640.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M640.642 1720.96 L640.642 1720.96 L640.924 1720.96 L640.924 1720.96 L640.642 1720.96 L640.642 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="640.642,1720.96 640.642,1720.96 640.924,1720.96 640.642,1720.96 "/>
<path clip-path="url(#clip322)" d="M640.924 1720.96 L640.924 1720.96 L641.205 1720.96 L641.205 1720.96 L640.924 1720.96 L640.924 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="640.924,1720.96 640.924,1720.96 641.205,1720.96 640.924,1720.96 "/>
<path clip-path="url(#clip322)" d="M641.205 1720.96 L641.205 1720.96 L641.487 1720.96 L641.487 1720.96 L641.205 1720.96 L641.205 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="641.205,1720.96 641.205,1720.96 641.487,1720.96 641.205,1720.96 "/>
<path clip-path="url(#clip322)" d="M641.487 1720.96 L641.487 1720.96 L641.769 1720.96 L641.769 1720.96 L641.487 1720.96 L641.487 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="641.487,1720.96 641.487,1720.96 641.769,1720.96 641.487,1720.96 "/>
<path clip-path="url(#clip322)" d="M641.769 1720.96 L641.769 1720.96 L642.05 1720.96 L642.05 1720.96 L641.769 1720.96 L641.769 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="641.769,1720.96 641.769,1720.96 642.05,1720.96 641.769,1720.96 "/>
<path clip-path="url(#clip322)" d="M642.05 1720.96 L642.05 1720.96 L642.332 1720.96 L642.332 1720.96 L642.05 1720.96 L642.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="642.05,1720.96 642.05,1720.96 642.332,1720.96 642.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M642.332 1720.96 L642.332 1720.96 L642.614 1720.96 L642.614 1720.96 L642.332 1720.96 L642.332 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="642.332,1720.96 642.332,1720.96 642.614,1720.96 642.332,1720.96 "/>
<path clip-path="url(#clip322)" d="M642.614 1720.96 L642.614 1720.96 L642.896 1720.96 L642.896 1720.96 L642.614 1720.96 L642.614 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="642.614,1720.96 642.614,1720.96 642.896,1720.96 642.614,1720.96 "/>
<path clip-path="url(#clip322)" d="M642.896 1720.96 L642.896 1720.96 L643.177 1720.96 L643.177 1720.96 L642.896 1720.96 L642.896 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="642.896,1720.96 642.896,1720.96 643.177,1720.96 642.896,1720.96 "/>
<path clip-path="url(#clip322)" d="M643.177 1720.96 L643.177 1720.96 L643.459 1720.96 L643.459 1720.96 L643.177 1720.96 L643.177 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="643.177,1720.96 643.177,1720.96 643.459,1720.96 643.177,1720.96 "/>
<path clip-path="url(#clip322)" d="M643.459 1720.96 L643.459 1720.96 L643.741 1720.96 L643.741 1720.96 L643.459 1720.96 L643.459 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="643.459,1720.96 643.459,1720.96 643.741,1720.96 643.459,1720.96 "/>
<path clip-path="url(#clip322)" d="M643.741 1720.96 L643.741 1720.96 L644.023 1720.96 L644.023 1720.96 L643.741 1720.96 L643.741 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="643.741,1720.96 643.741,1720.96 644.023,1720.96 643.741,1720.96 "/>
<path clip-path="url(#clip322)" d="M644.023 1720.96 L644.023 1720.96 L644.304 1720.96 L644.304 1720.96 L644.023 1720.96 L644.023 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="644.023,1720.96 644.023,1720.96 644.304,1720.96 644.023,1720.96 "/>
<path clip-path="url(#clip322)" d="M644.304 1720.96 L644.304 1720.96 L644.586 1720.96 L644.586 1720.96 L644.304 1720.96 L644.304 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="644.304,1720.96 644.304,1720.96 644.586,1720.96 644.304,1720.96 "/>
<path clip-path="url(#clip322)" d="M644.586 1720.96 L644.586 1720.96 L644.868 1720.96 L644.868 1720.96 L644.586 1720.96 L644.586 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="644.586,1720.96 644.586,1720.96 644.868,1720.96 644.586,1720.96 "/>
<path clip-path="url(#clip322)" d="M644.868 1720.96 L644.868 1720.96 L645.149 1720.96 L645.149 1720.96 L644.868 1720.96 L644.868 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="644.868,1720.96 644.868,1720.96 645.149,1720.96 644.868,1720.96 "/>
<path clip-path="url(#clip322)" d="M645.149 1720.96 L645.149 1720.96 L645.431 1720.96 L645.431 1720.96 L645.149 1720.96 L645.149 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="645.149,1720.96 645.149,1720.96 645.431,1720.96 645.149,1720.96 "/>
<path clip-path="url(#clip322)" d="M645.431 1720.96 L645.431 1720.96 L645.713 1720.96 L645.713 1720.96 L645.431 1720.96 L645.431 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="645.431,1720.96 645.431,1720.96 645.713,1720.96 645.431,1720.96 "/>
<path clip-path="url(#clip322)" d="M645.713 1720.96 L645.713 1720.96 L645.995 1720.96 L645.995 1720.96 L645.713 1720.96 L645.713 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="645.713,1720.96 645.713,1720.96 645.995,1720.96 645.713,1720.96 "/>
<path clip-path="url(#clip322)" d="M645.995 1720.96 L645.995 1720.96 L646.276 1720.96 L646.276 1720.96 L645.995 1720.96 L645.995 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="645.995,1720.96 645.995,1720.96 646.276,1720.96 645.995,1720.96 "/>
<path clip-path="url(#clip322)" d="M646.276 1720.96 L646.276 1720.96 L646.558 1720.96 L646.558 1720.96 L646.276 1720.96 L646.276 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="646.276,1720.96 646.276,1720.96 646.558,1720.96 646.276,1720.96 "/>
<path clip-path="url(#clip322)" d="M646.558 1720.96 L646.558 1720.96 L646.84 1720.96 L646.84 1720.96 L646.558 1720.96 L646.558 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="646.558,1720.96 646.558,1720.96 646.84,1720.96 646.558,1720.96 "/>
<path clip-path="url(#clip322)" d="M646.84 1720.96 L646.84 1720.96 L647.122 1720.96 L647.122 1720.96 L646.84 1720.96 L646.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="646.84,1720.96 646.84,1720.96 647.122,1720.96 646.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M647.122 1720.96 L647.122 1720.96 L647.403 1720.96 L647.403 1720.96 L647.122 1720.96 L647.122 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="647.122,1720.96 647.122,1720.96 647.403,1720.96 647.122,1720.96 "/>
<path clip-path="url(#clip322)" d="M647.403 1720.96 L647.403 1720.96 L647.685 1720.96 L647.685 1720.96 L647.403 1720.96 L647.403 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="647.403,1720.96 647.403,1720.96 647.685,1720.96 647.403,1720.96 "/>
<path clip-path="url(#clip322)" d="M647.685 1720.96 L647.685 1720.96 L647.967 1720.96 L647.967 1720.96 L647.685 1720.96 L647.685 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="647.685,1720.96 647.685,1720.96 647.967,1720.96 647.685,1720.96 "/>
<path clip-path="url(#clip322)" d="M647.967 1720.96 L647.967 1720.96 L648.248 1720.96 L648.248 1720.96 L647.967 1720.96 L647.967 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="647.967,1720.96 647.967,1720.96 648.248,1720.96 647.967,1720.96 "/>
<path clip-path="url(#clip322)" d="M648.248 1720.96 L648.248 1720.96 L648.53 1720.96 L648.53 1720.96 L648.248 1720.96 L648.248 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="648.248,1720.96 648.248,1720.96 648.53,1720.96 648.248,1720.96 "/>
<path clip-path="url(#clip322)" d="M648.53 1720.96 L648.53 1720.96 L648.812 1720.96 L648.812 1720.96 L648.53 1720.96 L648.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="648.53,1720.96 648.53,1720.96 648.812,1720.96 648.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M648.812 1720.96 L648.812 1720.96 L649.094 1720.96 L649.094 1720.96 L648.812 1720.96 L648.812 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="648.812,1720.96 648.812,1720.96 649.094,1720.96 648.812,1720.96 "/>
<path clip-path="url(#clip322)" d="M649.094 1720.96 L649.094 1720.96 L649.375 1720.96 L649.375 1720.96 L649.094 1720.96 L649.094 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="649.094,1720.96 649.094,1720.96 649.375,1720.96 649.094,1720.96 "/>
<path clip-path="url(#clip322)" d="M649.375 1720.96 L649.375 1720.96 L649.657 1720.96 L649.657 1720.96 L649.375 1720.96 L649.375 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="649.375,1720.96 649.375,1720.96 649.657,1720.96 649.375,1720.96 "/>
<path clip-path="url(#clip322)" d="M649.657 1720.96 L649.657 1720.96 L649.939 1720.96 L649.939 1720.96 L649.657 1720.96 L649.657 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="649.657,1720.96 649.657,1720.96 649.939,1720.96 649.657,1720.96 "/>
<path clip-path="url(#clip322)" d="M649.939 1720.96 L649.939 1720.96 L650.221 1720.96 L650.221 1720.96 L649.939 1720.96 L649.939 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="649.939,1720.96 649.939,1720.96 650.221,1720.96 649.939,1720.96 "/>
<path clip-path="url(#clip322)" d="M650.221 1720.96 L650.221 1720.96 L650.502 1720.96 L650.502 1720.96 L650.221 1720.96 L650.221 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="650.221,1720.96 650.221,1720.96 650.502,1720.96 650.221,1720.96 "/>
<path clip-path="url(#clip322)" d="M650.502 1720.96 L650.502 1720.96 L650.784 1720.96 L650.784 1720.96 L650.502 1720.96 L650.502 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="650.502,1720.96 650.502,1720.96 650.784,1720.96 650.502,1720.96 "/>
<path clip-path="url(#clip322)" d="M650.784 1720.96 L650.784 1720.96 L651.066 1720.96 L651.066 1720.96 L650.784 1720.96 L650.784 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="650.784,1720.96 650.784,1720.96 651.066,1720.96 650.784,1720.96 "/>
<path clip-path="url(#clip322)" d="M651.066 1720.96 L651.066 1720.96 L651.347 1720.96 L651.347 1720.96 L651.066 1720.96 L651.066 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="651.066,1720.96 651.066,1720.96 651.347,1720.96 651.066,1720.96 "/>
<path clip-path="url(#clip322)" d="M651.347 1720.96 L651.347 1720.96 L651.629 1720.96 L651.629 1720.96 L651.347 1720.96 L651.347 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="651.347,1720.96 651.347,1720.96 651.629,1720.96 651.347,1720.96 "/>
<path clip-path="url(#clip322)" d="M651.629 1720.96 L651.629 1720.96 L651.911 1720.96 L651.911 1720.96 L651.629 1720.96 L651.629 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="651.629,1720.96 651.629,1720.96 651.911,1720.96 651.629,1720.96 "/>
<path clip-path="url(#clip322)" d="M651.911 1720.96 L651.911 1720.96 L652.193 1720.96 L652.193 1720.96 L651.911 1720.96 L651.911 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="651.911,1720.96 651.911,1720.96 652.193,1720.96 651.911,1720.96 "/>
<path clip-path="url(#clip322)" d="M652.193 1720.96 L652.193 1720.96 L652.474 1720.96 L652.474 1720.96 L652.193 1720.96 L652.193 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="652.193,1720.96 652.193,1720.96 652.474,1720.96 652.193,1720.96 "/>
<path clip-path="url(#clip322)" d="M652.474 1720.96 L652.474 1720.96 L652.756 1720.96 L652.756 1720.96 L652.474 1720.96 L652.474 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="652.474,1720.96 652.474,1720.96 652.756,1720.96 652.474,1720.96 "/>
<path clip-path="url(#clip322)" d="M652.756 1720.96 L652.756 1720.96 L653.038 1720.96 L653.038 1720.96 L652.756 1720.96 L652.756 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="652.756,1720.96 652.756,1720.96 653.038,1720.96 652.756,1720.96 "/>
<path clip-path="url(#clip322)" d="M653.038 1720.96 L653.038 1720.96 L653.319 1720.96 L653.319 1720.96 L653.038 1720.96 L653.038 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="653.038,1720.96 653.038,1720.96 653.319,1720.96 653.038,1720.96 "/>
<path clip-path="url(#clip322)" d="M653.319 1720.96 L653.319 1720.96 L653.601 1720.96 L653.601 1720.96 L653.319 1720.96 L653.319 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="653.319,1720.96 653.319,1720.96 653.601,1720.96 653.319,1720.96 "/>
<path clip-path="url(#clip322)" d="M653.601 1720.96 L653.601 1720.96 L653.883 1720.96 L653.883 1720.96 L653.601 1720.96 L653.601 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="653.601,1720.96 653.601,1720.96 653.883,1720.96 653.601,1720.96 "/>
<path clip-path="url(#clip322)" d="M653.883 1720.96 L653.883 1720.96 L654.165 1720.96 L654.165 1720.96 L653.883 1720.96 L653.883 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="653.883,1720.96 653.883,1720.96 654.165,1720.96 653.883,1720.96 "/>
<path clip-path="url(#clip322)" d="M654.165 1720.96 L654.165 1720.96 L654.446 1720.96 L654.446 1720.96 L654.165 1720.96 L654.165 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="654.165,1720.96 654.165,1720.96 654.446,1720.96 654.165,1720.96 "/>
<path clip-path="url(#clip322)" d="M654.446 1720.96 L654.446 1720.96 L654.728 1720.96 L654.728 1720.96 L654.446 1720.96 L654.446 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="654.446,1720.96 654.446,1720.96 654.728,1720.96 654.446,1720.96 "/>
<path clip-path="url(#clip322)" d="M654.728 1720.96 L654.728 1720.96 L655.01 1720.96 L655.01 1720.96 L654.728 1720.96 L654.728 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="654.728,1720.96 654.728,1720.96 655.01,1720.96 654.728,1720.96 "/>
<path clip-path="url(#clip322)" d="M655.01 1720.96 L655.01 1720.96 L655.292 1720.96 L655.292 1720.96 L655.01 1720.96 L655.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="655.01,1720.96 655.01,1720.96 655.292,1720.96 655.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M655.292 1720.96 L655.292 1720.96 L655.573 1720.96 L655.573 1720.96 L655.292 1720.96 L655.292 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="655.292,1720.96 655.292,1720.96 655.573,1720.96 655.292,1720.96 "/>
<path clip-path="url(#clip322)" d="M655.573 1720.96 L655.573 1720.96 L655.855 1720.96 L655.855 1720.96 L655.573 1720.96 L655.573 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="655.573,1720.96 655.573,1720.96 655.855,1720.96 655.573,1720.96 "/>
<path clip-path="url(#clip322)" d="M655.855 1720.96 L655.855 1720.96 L656.137 1720.96 L656.137 1720.96 L655.855 1720.96 L655.855 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="655.855,1720.96 655.855,1720.96 656.137,1720.96 655.855,1720.96 "/>
<path clip-path="url(#clip322)" d="M656.137 1720.96 L656.137 1720.96 L656.418 1720.96 L656.418 1720.96 L656.137 1720.96 L656.137 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="656.137,1720.96 656.137,1720.96 656.418,1720.96 656.137,1720.96 "/>
<path clip-path="url(#clip322)" d="M656.418 1720.96 L656.418 1720.96 L656.7 1720.96 L656.7 1720.96 L656.418 1720.96 L656.418 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="656.418,1720.96 656.418,1720.96 656.7,1720.96 656.418,1720.96 "/>
<path clip-path="url(#clip322)" d="M656.7 1720.96 L656.7 1720.96 L656.982 1720.96 L656.982 1720.96 L656.7 1720.96 L656.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="656.7,1720.96 656.7,1720.96 656.982,1720.96 656.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M656.982 1720.96 L656.982 1720.96 L657.264 1720.96 L657.264 1720.96 L656.982 1720.96 L656.982 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="656.982,1720.96 656.982,1720.96 657.264,1720.96 656.982,1720.96 "/>
<path clip-path="url(#clip322)" d="M657.264 1720.96 L657.264 1720.96 L657.545 1720.96 L657.545 1720.96 L657.264 1720.96 L657.264 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="657.264,1720.96 657.264,1720.96 657.545,1720.96 657.264,1720.96 "/>
<path clip-path="url(#clip322)" d="M657.545 1720.96 L657.545 1720.96 L657.827 1720.96 L657.827 1720.96 L657.545 1720.96 L657.545 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="657.545,1720.96 657.545,1720.96 657.827,1720.96 657.545,1720.96 "/>
<path clip-path="url(#clip322)" d="M657.827 1720.96 L657.827 1720.96 L658.109 1720.96 L658.109 1720.96 L657.827 1720.96 L657.827 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="657.827,1720.96 657.827,1720.96 658.109,1720.96 657.827,1720.96 "/>
<path clip-path="url(#clip322)" d="M658.109 1720.96 L658.109 1720.96 L658.391 1720.96 L658.391 1720.96 L658.109 1720.96 L658.109 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="658.109,1720.96 658.109,1720.96 658.391,1720.96 658.109,1720.96 "/>
<path clip-path="url(#clip322)" d="M658.391 1720.96 L658.391 1720.96 L658.672 1720.96 L658.672 1720.96 L658.391 1720.96 L658.391 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="658.391,1720.96 658.391,1720.96 658.672,1720.96 658.391,1720.96 "/>
<path clip-path="url(#clip322)" d="M658.672 1720.96 L658.672 1720.96 L658.954 1720.96 L658.954 1720.96 L658.672 1720.96 L658.672 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="658.672,1720.96 658.672,1720.96 658.954,1720.96 658.672,1720.96 "/>
<path clip-path="url(#clip322)" d="M658.954 1720.96 L658.954 1720.96 L659.236 1720.96 L659.236 1720.96 L658.954 1720.96 L658.954 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="658.954,1720.96 658.954,1720.96 659.236,1720.96 658.954,1720.96 "/>
<path clip-path="url(#clip322)" d="M659.236 1720.96 L659.236 1720.96 L659.517 1720.96 L659.517 1720.96 L659.236 1720.96 L659.236 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="659.236,1720.96 659.236,1720.96 659.517,1720.96 659.236,1720.96 "/>
<path clip-path="url(#clip322)" d="M659.517 1720.96 L659.517 1720.96 L659.799 1720.96 L659.799 1720.96 L659.517 1720.96 L659.517 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="659.517,1720.96 659.517,1720.96 659.799,1720.96 659.517,1720.96 "/>
<path clip-path="url(#clip322)" d="M659.799 1720.96 L659.799 1720.96 L660.081 1720.96 L660.081 1720.96 L659.799 1720.96 L659.799 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="659.799,1720.96 659.799,1720.96 660.081,1720.96 659.799,1720.96 "/>
<path clip-path="url(#clip322)" d="M660.081 1720.96 L660.081 1720.96 L660.363 1720.96 L660.363 1720.96 L660.081 1720.96 L660.081 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="660.081,1720.96 660.081,1720.96 660.363,1720.96 660.081,1720.96 "/>
<path clip-path="url(#clip322)" d="M660.363 1720.96 L660.363 1720.96 L660.644 1720.96 L660.644 1720.96 L660.363 1720.96 L660.363 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="660.363,1720.96 660.363,1720.96 660.644,1720.96 660.363,1720.96 "/>
<path clip-path="url(#clip322)" d="M660.644 1720.96 L660.644 1720.96 L660.926 1720.96 L660.926 1720.96 L660.644 1720.96 L660.644 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="660.644,1720.96 660.644,1720.96 660.926,1720.96 660.644,1720.96 "/>
<path clip-path="url(#clip322)" d="M660.926 1720.96 L660.926 1720.96 L661.208 1720.96 L661.208 1720.96 L660.926 1720.96 L660.926 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="660.926,1720.96 660.926,1720.96 661.208,1720.96 660.926,1720.96 "/>
<path clip-path="url(#clip322)" d="M661.208 1720.96 L661.208 1720.96 L661.49 1720.96 L661.49 1720.96 L661.208 1720.96 L661.208 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="661.208,1720.96 661.208,1720.96 661.49,1720.96 661.208,1720.96 "/>
<path clip-path="url(#clip322)" d="M661.49 1720.96 L661.49 1720.96 L661.771 1720.96 L661.771 1720.96 L661.49 1720.96 L661.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="661.49,1720.96 661.49,1720.96 661.771,1720.96 661.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M661.771 1720.96 L661.771 1720.96 L662.053 1720.96 L662.053 1720.96 L661.771 1720.96 L661.771 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="661.771,1720.96 661.771,1720.96 662.053,1720.96 661.771,1720.96 "/>
<path clip-path="url(#clip322)" d="M662.053 1720.96 L662.053 1720.96 L662.335 1720.96 L662.335 1720.96 L662.053 1720.96 L662.053 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="662.053,1720.96 662.053,1720.96 662.335,1720.96 662.053,1720.96 "/>
<path clip-path="url(#clip322)" d="M662.335 1720.96 L662.335 1720.96 L662.616 1720.96 L662.616 1720.96 L662.335 1720.96 L662.335 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="662.335,1720.96 662.335,1720.96 662.616,1720.96 662.335,1720.96 "/>
<path clip-path="url(#clip322)" d="M662.616 1720.96 L662.616 1720.96 L662.898 1720.96 L662.898 1720.96 L662.616 1720.96 L662.616 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="662.616,1720.96 662.616,1720.96 662.898,1720.96 662.616,1720.96 "/>
<path clip-path="url(#clip322)" d="M662.898 1720.96 L662.898 1720.96 L663.18 1720.96 L663.18 1720.96 L662.898 1720.96 L662.898 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="662.898,1720.96 662.898,1720.96 663.18,1720.96 662.898,1720.96 "/>
<path clip-path="url(#clip322)" d="M663.18 1720.96 L663.18 1720.96 L663.462 1720.96 L663.462 1720.96 L663.18 1720.96 L663.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="663.18,1720.96 663.18,1720.96 663.462,1720.96 663.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M663.462 1720.96 L663.462 1720.96 L663.743 1720.96 L663.743 1720.96 L663.462 1720.96 L663.462 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="663.462,1720.96 663.462,1720.96 663.743,1720.96 663.462,1720.96 "/>
<path clip-path="url(#clip322)" d="M663.743 1720.96 L663.743 1720.96 L664.025 1720.96 L664.025 1720.96 L663.743 1720.96 L663.743 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="663.743,1720.96 663.743,1720.96 664.025,1720.96 663.743,1720.96 "/>
<path clip-path="url(#clip322)" d="M664.025 1720.96 L664.025 1720.96 L664.307 1720.96 L664.307 1720.96 L664.025 1720.96 L664.025 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="664.025,1720.96 664.025,1720.96 664.307,1720.96 664.025,1720.96 "/>
<path clip-path="url(#clip322)" d="M664.307 1720.96 L664.307 1720.96 L664.589 1720.96 L664.589 1720.96 L664.307 1720.96 L664.307 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="664.307,1720.96 664.307,1720.96 664.589,1720.96 664.307,1720.96 "/>
<path clip-path="url(#clip322)" d="M664.589 1720.96 L664.589 1720.96 L664.87 1720.96 L664.87 1720.96 L664.589 1720.96 L664.589 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="664.589,1720.96 664.589,1720.96 664.87,1720.96 664.589,1720.96 "/>
<path clip-path="url(#clip322)" d="M664.87 1720.96 L664.87 1720.96 L665.152 1720.96 L665.152 1720.96 L664.87 1720.96 L664.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="664.87,1720.96 664.87,1720.96 665.152,1720.96 664.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M665.152 1720.96 L665.152 1720.96 L665.434 1720.96 L665.434 1720.96 L665.152 1720.96 L665.152 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="665.152,1720.96 665.152,1720.96 665.434,1720.96 665.152,1720.96 "/>
<path clip-path="url(#clip322)" d="M665.434 1720.96 L665.434 1720.96 L665.715 1720.96 L665.715 1720.96 L665.434 1720.96 L665.434 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="665.434,1720.96 665.434,1720.96 665.715,1720.96 665.434,1720.96 "/>
<path clip-path="url(#clip322)" d="M665.715 1720.96 L665.715 1720.96 L665.997 1720.96 L665.997 1720.96 L665.715 1720.96 L665.715 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="665.715,1720.96 665.715,1720.96 665.997,1720.96 665.715,1720.96 "/>
<path clip-path="url(#clip322)" d="M665.997 1720.96 L665.997 1720.96 L666.279 1720.96 L666.279 1720.96 L665.997 1720.96 L665.997 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="665.997,1720.96 665.997,1720.96 666.279,1720.96 665.997,1720.96 "/>
<path clip-path="url(#clip322)" d="M666.279 1720.96 L666.279 1720.96 L666.561 1720.96 L666.561 1720.96 L666.279 1720.96 L666.279 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="666.279,1720.96 666.279,1720.96 666.561,1720.96 666.279,1720.96 "/>
<path clip-path="url(#clip322)" d="M666.561 1720.96 L666.561 1720.96 L666.842 1720.96 L666.842 1720.96 L666.561 1720.96 L666.561 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="666.561,1720.96 666.561,1720.96 666.842,1720.96 666.561,1720.96 "/>
<path clip-path="url(#clip322)" d="M666.842 1720.96 L666.842 1720.96 L667.124 1720.96 L667.124 1720.96 L666.842 1720.96 L666.842 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="666.842,1720.96 666.842,1720.96 667.124,1720.96 666.842,1720.96 "/>
<path clip-path="url(#clip322)" d="M667.124 1720.96 L667.124 1720.96 L667.406 1720.96 L667.406 1720.96 L667.124 1720.96 L667.124 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="667.124,1720.96 667.124,1720.96 667.406,1720.96 667.124,1720.96 "/>
<path clip-path="url(#clip322)" d="M667.406 1720.96 L667.406 1720.96 L667.687 1720.96 L667.687 1720.96 L667.406 1720.96 L667.406 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="667.406,1720.96 667.406,1720.96 667.687,1720.96 667.406,1720.96 "/>
<path clip-path="url(#clip322)" d="M667.687 1720.96 L667.687 1720.96 L667.969 1720.96 L667.969 1720.96 L667.687 1720.96 L667.687 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="667.687,1720.96 667.687,1720.96 667.969,1720.96 667.687,1720.96 "/>
<path clip-path="url(#clip322)" d="M667.969 1720.96 L667.969 1720.96 L668.251 1720.96 L668.251 1720.96 L667.969 1720.96 L667.969 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="667.969,1720.96 667.969,1720.96 668.251,1720.96 667.969,1720.96 "/>
<path clip-path="url(#clip322)" d="M668.251 1720.96 L668.251 1720.96 L668.533 1720.96 L668.533 1720.96 L668.251 1720.96 L668.251 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="668.251,1720.96 668.251,1720.96 668.533,1720.96 668.251,1720.96 "/>
<path clip-path="url(#clip322)" d="M668.533 1720.96 L668.533 1720.96 L668.814 1720.96 L668.814 1720.96 L668.533 1720.96 L668.533 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="668.533,1720.96 668.533,1720.96 668.814,1720.96 668.533,1720.96 "/>
<path clip-path="url(#clip322)" d="M668.814 1720.96 L668.814 1720.96 L669.096 1720.96 L669.096 1720.96 L668.814 1720.96 L668.814 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="668.814,1720.96 668.814,1720.96 669.096,1720.96 668.814,1720.96 "/>
<path clip-path="url(#clip322)" d="M669.096 1720.96 L669.096 1720.96 L669.378 1720.96 L669.378 1720.96 L669.096 1720.96 L669.096 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="669.096,1720.96 669.096,1720.96 669.378,1720.96 669.096,1720.96 "/>
<path clip-path="url(#clip322)" d="M669.378 1720.96 L669.378 1720.96 L669.66 1720.96 L669.66 1720.96 L669.378 1720.96 L669.378 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="669.378,1720.96 669.378,1720.96 669.66,1720.96 669.378,1720.96 "/>
<path clip-path="url(#clip322)" d="M669.66 1720.96 L669.66 1720.96 L669.941 1720.96 L669.941 1720.96 L669.66 1720.96 L669.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="669.66,1720.96 669.66,1720.96 669.941,1720.96 669.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M669.941 1720.96 L669.941 1720.96 L670.223 1720.96 L670.223 1720.96 L669.941 1720.96 L669.941 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="669.941,1720.96 669.941,1720.96 670.223,1720.96 669.941,1720.96 "/>
<path clip-path="url(#clip322)" d="M670.223 1720.96 L670.223 1720.96 L670.505 1720.96 L670.505 1720.96 L670.223 1720.96 L670.223 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="670.223,1720.96 670.223,1720.96 670.505,1720.96 670.223,1720.96 "/>
<path clip-path="url(#clip322)" d="M670.505 1720.96 L670.505 1720.96 L670.786 1720.96 L670.786 1720.96 L670.505 1720.96 L670.505 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="670.505,1720.96 670.505,1720.96 670.786,1720.96 670.505,1720.96 "/>
<path clip-path="url(#clip322)" d="M670.786 1720.96 L670.786 1720.96 L671.068 1720.96 L671.068 1720.96 L670.786 1720.96 L670.786 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="670.786,1720.96 670.786,1720.96 671.068,1720.96 670.786,1720.96 "/>
<path clip-path="url(#clip322)" d="M671.068 1720.96 L671.068 1720.96 L671.35 1720.96 L671.35 1720.96 L671.068 1720.96 L671.068 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="671.068,1720.96 671.068,1720.96 671.35,1720.96 671.068,1720.96 "/>
<path clip-path="url(#clip322)" d="M671.35 1720.96 L671.35 1720.96 L671.632 1720.96 L671.632 1720.96 L671.35 1720.96 L671.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="671.35,1720.96 671.35,1720.96 671.632,1720.96 671.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M671.632 1720.96 L671.632 1720.96 L671.913 1720.96 L671.913 1720.96 L671.632 1720.96 L671.632 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="671.632,1720.96 671.632,1720.96 671.913,1720.96 671.632,1720.96 "/>
<path clip-path="url(#clip322)" d="M671.913 1720.96 L671.913 1720.96 L672.195 1720.96 L672.195 1720.96 L671.913 1720.96 L671.913 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="671.913,1720.96 671.913,1720.96 672.195,1720.96 671.913,1720.96 "/>
<path clip-path="url(#clip322)" d="M672.195 1720.96 L672.195 1720.96 L672.477 1720.96 L672.477 1720.96 L672.195 1720.96 L672.195 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="672.195,1720.96 672.195,1720.96 672.477,1720.96 672.195,1720.96 "/>
<path clip-path="url(#clip322)" d="M672.477 1720.96 L672.477 1720.96 L672.759 1720.96 L672.759 1720.96 L672.477 1720.96 L672.477 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="672.477,1720.96 672.477,1720.96 672.759,1720.96 672.477,1720.96 "/>
<path clip-path="url(#clip322)" d="M672.759 1720.96 L672.759 1720.96 L673.04 1720.96 L673.04 1720.96 L672.759 1720.96 L672.759 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="672.759,1720.96 672.759,1720.96 673.04,1720.96 672.759,1720.96 "/>
<path clip-path="url(#clip322)" d="M673.04 1720.96 L673.04 1720.96 L673.322 1720.96 L673.322 1720.96 L673.04 1720.96 L673.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="673.04,1720.96 673.04,1720.96 673.322,1720.96 673.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M673.322 1720.96 L673.322 1720.96 L673.604 1720.96 L673.604 1720.96 L673.322 1720.96 L673.322 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="673.322,1720.96 673.322,1720.96 673.604,1720.96 673.322,1720.96 "/>
<path clip-path="url(#clip322)" d="M673.604 1720.96 L673.604 1720.96 L673.885 1720.96 L673.885 1720.96 L673.604 1720.96 L673.604 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="673.604,1720.96 673.604,1720.96 673.885,1720.96 673.604,1720.96 "/>
<path clip-path="url(#clip322)" d="M673.885 1720.96 L673.885 1720.96 L674.167 1720.96 L674.167 1720.96 L673.885 1720.96 L673.885 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="673.885,1720.96 673.885,1720.96 674.167,1720.96 673.885,1720.96 "/>
<path clip-path="url(#clip322)" d="M674.167 1720.96 L674.167 1720.96 L674.449 1720.96 L674.449 1720.96 L674.167 1720.96 L674.167 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="674.167,1720.96 674.167,1720.96 674.449,1720.96 674.167,1720.96 "/>
<path clip-path="url(#clip322)" d="M674.449 1720.96 L674.449 1720.96 L674.731 1720.96 L674.731 1720.96 L674.449 1720.96 L674.449 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="674.449,1720.96 674.449,1720.96 674.731,1720.96 674.449,1720.96 "/>
<path clip-path="url(#clip322)" d="M674.731 1720.96 L674.731 1720.96 L675.012 1720.96 L675.012 1720.96 L674.731 1720.96 L674.731 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="674.731,1720.96 674.731,1720.96 675.012,1720.96 674.731,1720.96 "/>
<path clip-path="url(#clip322)" d="M675.012 1720.96 L675.012 1720.96 L675.294 1720.96 L675.294 1720.96 L675.012 1720.96 L675.012 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="675.012,1720.96 675.012,1720.96 675.294,1720.96 675.012,1720.96 "/>
<path clip-path="url(#clip322)" d="M675.294 1720.96 L675.294 1720.96 L675.576 1720.96 L675.576 1720.96 L675.294 1720.96 L675.294 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="675.294,1720.96 675.294,1720.96 675.576,1720.96 675.294,1720.96 "/>
<path clip-path="url(#clip322)" d="M675.576 1720.96 L675.576 1720.96 L675.858 1720.96 L675.858 1720.96 L675.576 1720.96 L675.576 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="675.576,1720.96 675.576,1720.96 675.858,1720.96 675.576,1720.96 "/>
<path clip-path="url(#clip322)" d="M675.858 1720.96 L675.858 1720.96 L676.139 1720.96 L676.139 1720.96 L675.858 1720.96 L675.858 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="675.858,1720.96 675.858,1720.96 676.139,1720.96 675.858,1720.96 "/>
<path clip-path="url(#clip322)" d="M676.139 1720.96 L676.139 1720.96 L676.421 1720.96 L676.421 1720.96 L676.139 1720.96 L676.139 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="676.139,1720.96 676.139,1720.96 676.421,1720.96 676.139,1720.96 "/>
<path clip-path="url(#clip322)" d="M676.421 1720.96 L676.421 1720.96 L676.703 1720.96 L676.703 1720.96 L676.421 1720.96 L676.421 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="676.421,1720.96 676.421,1720.96 676.703,1720.96 676.421,1720.96 "/>
<path clip-path="url(#clip322)" d="M676.703 1720.96 L676.703 1720.96 L676.984 1720.96 L676.984 1720.96 L676.703 1720.96 L676.703 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="676.703,1720.96 676.703,1720.96 676.984,1720.96 676.703,1720.96 "/>
<path clip-path="url(#clip322)" d="M676.984 1720.96 L676.984 1720.96 L677.266 1720.96 L677.266 1720.96 L676.984 1720.96 L676.984 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="676.984,1720.96 676.984,1720.96 677.266,1720.96 676.984,1720.96 "/>
<path clip-path="url(#clip322)" d="M677.266 1720.96 L677.266 1720.96 L677.548 1720.96 L677.548 1720.96 L677.266 1720.96 L677.266 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="677.266,1720.96 677.266,1720.96 677.548,1720.96 677.266,1720.96 "/>
<path clip-path="url(#clip322)" d="M677.548 1720.96 L677.548 1720.96 L677.83 1720.96 L677.83 1720.96 L677.548 1720.96 L677.548 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="677.548,1720.96 677.548,1720.96 677.83,1720.96 677.548,1720.96 "/>
<path clip-path="url(#clip322)" d="M677.83 1720.96 L677.83 1720.96 L678.111 1720.96 L678.111 1720.96 L677.83 1720.96 L677.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="677.83,1720.96 677.83,1720.96 678.111,1720.96 677.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M678.111 1720.96 L678.111 1720.96 L678.393 1720.96 L678.393 1720.96 L678.111 1720.96 L678.111 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="678.111,1720.96 678.111,1720.96 678.393,1720.96 678.111,1720.96 "/>
<path clip-path="url(#clip322)" d="M678.393 1720.96 L678.393 1720.96 L678.675 1720.96 L678.675 1720.96 L678.393 1720.96 L678.393 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="678.393,1720.96 678.393,1720.96 678.675,1720.96 678.393,1720.96 "/>
<path clip-path="url(#clip322)" d="M678.675 1720.96 L678.675 1720.96 L678.957 1720.96 L678.957 1720.96 L678.675 1720.96 L678.675 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="678.675,1720.96 678.675,1720.96 678.957,1720.96 678.675,1720.96 "/>
<path clip-path="url(#clip322)" d="M678.957 1720.96 L678.957 1720.96 L679.238 1720.96 L679.238 1720.96 L678.957 1720.96 L678.957 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="678.957,1720.96 678.957,1720.96 679.238,1720.96 678.957,1720.96 "/>
<path clip-path="url(#clip322)" d="M679.238 1720.96 L679.238 1720.96 L679.52 1720.96 L679.52 1720.96 L679.238 1720.96 L679.238 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="679.238,1720.96 679.238,1720.96 679.52,1720.96 679.238,1720.96 "/>
<path clip-path="url(#clip322)" d="M679.52 1720.96 L679.52 1720.96 L679.802 1720.96 L679.802 1720.96 L679.52 1720.96 L679.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="679.52,1720.96 679.52,1720.96 679.802,1720.96 679.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M679.802 1720.96 L679.802 1720.96 L680.083 1720.96 L680.083 1720.96 L679.802 1720.96 L679.802 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="679.802,1720.96 679.802,1720.96 680.083,1720.96 679.802,1720.96 "/>
<path clip-path="url(#clip322)" d="M680.083 1720.96 L680.083 1720.96 L680.365 1720.96 L680.365 1720.96 L680.083 1720.96 L680.083 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="680.083,1720.96 680.083,1720.96 680.365,1720.96 680.083,1720.96 "/>
<path clip-path="url(#clip322)" d="M680.365 1720.96 L680.365 1720.96 L680.647 1720.96 L680.647 1720.96 L680.365 1720.96 L680.365 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="680.365,1720.96 680.365,1720.96 680.647,1720.96 680.365,1720.96 "/>
<path clip-path="url(#clip322)" d="M680.647 1720.96 L680.647 1720.96 L680.929 1720.96 L680.929 1720.96 L680.647 1720.96 L680.647 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="680.647,1720.96 680.647,1720.96 680.929,1720.96 680.647,1720.96 "/>
<path clip-path="url(#clip322)" d="M680.929 1720.96 L680.929 1720.96 L681.21 1720.96 L681.21 1720.96 L680.929 1720.96 L680.929 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="680.929,1720.96 680.929,1720.96 681.21,1720.96 680.929,1720.96 "/>
<path clip-path="url(#clip322)" d="M681.21 1720.96 L681.21 1720.96 L681.492 1720.96 L681.492 1720.96 L681.21 1720.96 L681.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="681.21,1720.96 681.21,1720.96 681.492,1720.96 681.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M681.492 1720.96 L681.492 1720.96 L681.774 1720.96 L681.774 1720.96 L681.492 1720.96 L681.492 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="681.492,1720.96 681.492,1720.96 681.774,1720.96 681.492,1720.96 "/>
<path clip-path="url(#clip322)" d="M681.774 1720.96 L681.774 1720.96 L682.056 1720.96 L682.056 1720.96 L681.774 1720.96 L681.774 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="681.774,1720.96 681.774,1720.96 682.056,1720.96 681.774,1720.96 "/>
<path clip-path="url(#clip322)" d="M682.056 1720.96 L682.056 1720.96 L682.337 1720.96 L682.337 1720.96 L682.056 1720.96 L682.056 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="682.056,1720.96 682.056,1720.96 682.337,1720.96 682.056,1720.96 "/>
<path clip-path="url(#clip322)" d="M682.337 1720.96 L682.337 1720.96 L682.619 1720.96 L682.619 1720.96 L682.337 1720.96 L682.337 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="682.337,1720.96 682.337,1720.96 682.619,1720.96 682.337,1720.96 "/>
<path clip-path="url(#clip322)" d="M682.619 1720.96 L682.619 1720.96 L682.901 1720.96 L682.901 1720.96 L682.619 1720.96 L682.619 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="682.619,1720.96 682.619,1720.96 682.901,1720.96 682.619,1720.96 "/>
<path clip-path="url(#clip322)" d="M682.901 1720.96 L682.901 1720.96 L683.182 1720.96 L683.182 1720.96 L682.901 1720.96 L682.901 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="682.901,1720.96 682.901,1720.96 683.182,1720.96 682.901,1720.96 "/>
<path clip-path="url(#clip322)" d="M683.182 1720.96 L683.182 1720.96 L683.464 1720.96 L683.464 1720.96 L683.182 1720.96 L683.182 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="683.182,1720.96 683.182,1720.96 683.464,1720.96 683.182,1720.96 "/>
<path clip-path="url(#clip322)" d="M683.464 1720.96 L683.464 1720.96 L683.746 1720.96 L683.746 1720.96 L683.464 1720.96 L683.464 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="683.464,1720.96 683.464,1720.96 683.746,1720.96 683.464,1720.96 "/>
<path clip-path="url(#clip322)" d="M683.746 1720.96 L683.746 1720.96 L684.028 1720.96 L684.028 1720.96 L683.746 1720.96 L683.746 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="683.746,1720.96 683.746,1720.96 684.028,1720.96 683.746,1720.96 "/>
<path clip-path="url(#clip322)" d="M684.028 1720.96 L684.028 1720.96 L684.309 1720.96 L684.309 1720.96 L684.028 1720.96 L684.028 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="684.028,1720.96 684.028,1720.96 684.309,1720.96 684.028,1720.96 "/>
<path clip-path="url(#clip322)" d="M684.309 1720.96 L684.309 1720.96 L684.591 1720.96 L684.591 1720.96 L684.309 1720.96 L684.309 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="684.309,1720.96 684.309,1720.96 684.591,1720.96 684.309,1720.96 "/>
<path clip-path="url(#clip322)" d="M684.591 1720.96 L684.591 1720.96 L684.873 1720.96 L684.873 1720.96 L684.591 1720.96 L684.591 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="684.591,1720.96 684.591,1720.96 684.873,1720.96 684.591,1720.96 "/>
<path clip-path="url(#clip322)" d="M684.873 1720.96 L684.873 1720.96 L685.154 1720.96 L685.154 1720.96 L684.873 1720.96 L684.873 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="684.873,1720.96 684.873,1720.96 685.154,1720.96 684.873,1720.96 "/>
<path clip-path="url(#clip322)" d="M685.154 1720.96 L685.154 1720.96 L685.436 1720.96 L685.436 1720.96 L685.154 1720.96 L685.154 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="685.154,1720.96 685.154,1720.96 685.436,1720.96 685.154,1720.96 "/>
<path clip-path="url(#clip322)" d="M685.436 1720.96 L685.436 1720.96 L685.718 1720.96 L685.718 1720.96 L685.436 1720.96 L685.436 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="685.436,1720.96 685.436,1720.96 685.718,1720.96 685.436,1720.96 "/>
<path clip-path="url(#clip322)" d="M685.718 1720.96 L685.718 1720.96 L686 1720.96 L686 1720.96 L685.718 1720.96 L685.718 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="685.718,1720.96 685.718,1720.96 686,1720.96 685.718,1720.96 "/>
<path clip-path="url(#clip322)" d="M686 1720.96 L686 1720.96 L686.281 1720.96 L686.281 1720.96 L686 1720.96 L686 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="686,1720.96 686,1720.96 686.281,1720.96 686,1720.96 "/>
<path clip-path="url(#clip322)" d="M686.281 1720.96 L686.281 1720.96 L686.563 1720.96 L686.563 1720.96 L686.281 1720.96 L686.281 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="686.281,1720.96 686.281,1720.96 686.563,1720.96 686.281,1720.96 "/>
<path clip-path="url(#clip322)" d="M686.563 1720.96 L686.563 1720.96 L686.845 1720.96 L686.845 1720.96 L686.563 1720.96 L686.563 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="686.563,1720.96 686.563,1720.96 686.845,1720.96 686.563,1720.96 "/>
<path clip-path="url(#clip322)" d="M686.845 1720.96 L686.845 1720.96 L687.127 1720.96 L687.127 1720.96 L686.845 1720.96 L686.845 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="686.845,1720.96 686.845,1720.96 687.127,1720.96 686.845,1720.96 "/>
<path clip-path="url(#clip322)" d="M687.127 1720.96 L687.127 1720.96 L687.408 1720.96 L687.408 1720.96 L687.127 1720.96 L687.127 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="687.127,1720.96 687.127,1720.96 687.408,1720.96 687.127,1720.96 "/>
<path clip-path="url(#clip322)" d="M687.408 1720.96 L687.408 1720.96 L687.69 1720.96 L687.69 1720.96 L687.408 1720.96 L687.408 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="687.408,1720.96 687.408,1720.96 687.69,1720.96 687.408,1720.96 "/>
<path clip-path="url(#clip322)" d="M687.69 1720.96 L687.69 1720.96 L687.972 1720.96 L687.972 1720.96 L687.69 1720.96 L687.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="687.69,1720.96 687.69,1720.96 687.972,1720.96 687.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M687.972 1720.96 L687.972 1720.96 L688.253 1720.96 L688.253 1720.96 L687.972 1720.96 L687.972 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="687.972,1720.96 687.972,1720.96 688.253,1720.96 687.972,1720.96 "/>
<path clip-path="url(#clip322)" d="M688.253 1720.96 L688.253 1720.96 L688.535 1720.96 L688.535 1720.96 L688.253 1720.96 L688.253 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="688.253,1720.96 688.253,1720.96 688.535,1720.96 688.253,1720.96 "/>
<path clip-path="url(#clip322)" d="M688.535 1720.96 L688.535 1720.96 L688.817 1720.96 L688.817 1720.96 L688.535 1720.96 L688.535 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="688.535,1720.96 688.535,1720.96 688.817,1720.96 688.535,1720.96 "/>
<path clip-path="url(#clip322)" d="M688.817 1720.96 L688.817 1720.96 L689.099 1720.96 L689.099 1720.96 L688.817 1720.96 L688.817 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="688.817,1720.96 688.817,1720.96 689.099,1720.96 688.817,1720.96 "/>
<path clip-path="url(#clip322)" d="M689.099 1720.96 L689.099 1720.96 L689.38 1720.96 L689.38 1720.96 L689.099 1720.96 L689.099 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="689.099,1720.96 689.099,1720.96 689.38,1720.96 689.099,1720.96 "/>
<path clip-path="url(#clip322)" d="M689.38 1720.96 L689.38 1720.96 L689.662 1720.96 L689.662 1720.96 L689.38 1720.96 L689.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="689.38,1720.96 689.38,1720.96 689.662,1720.96 689.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M689.662 1720.96 L689.662 1720.96 L689.944 1720.96 L689.944 1720.96 L689.662 1720.96 L689.662 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="689.662,1720.96 689.662,1720.96 689.944,1720.96 689.662,1720.96 "/>
<path clip-path="url(#clip322)" d="M689.944 1720.96 L689.944 1720.96 L690.226 1720.96 L690.226 1720.96 L689.944 1720.96 L689.944 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="689.944,1720.96 689.944,1720.96 690.226,1720.96 689.944,1720.96 "/>
<path clip-path="url(#clip322)" d="M690.226 1720.96 L690.226 1720.96 L690.507 1720.96 L690.507 1720.96 L690.226 1720.96 L690.226 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="690.226,1720.96 690.226,1720.96 690.507,1720.96 690.226,1720.96 "/>
<path clip-path="url(#clip322)" d="M690.507 1720.96 L690.507 1720.96 L690.789 1720.96 L690.789 1720.96 L690.507 1720.96 L690.507 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="690.507,1720.96 690.507,1720.96 690.789,1720.96 690.507,1720.96 "/>
<path clip-path="url(#clip322)" d="M690.789 1720.96 L690.789 1720.96 L691.071 1720.96 L691.071 1720.96 L690.789 1720.96 L690.789 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="690.789,1720.96 690.789,1720.96 691.071,1720.96 690.789,1720.96 "/>
<path clip-path="url(#clip322)" d="M691.071 1720.96 L691.071 1720.96 L691.352 1720.96 L691.352 1720.96 L691.071 1720.96 L691.071 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="691.071,1720.96 691.071,1720.96 691.352,1720.96 691.071,1720.96 "/>
<path clip-path="url(#clip322)" d="M691.352 1720.96 L691.352 1720.96 L691.634 1720.96 L691.634 1720.96 L691.352 1720.96 L691.352 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="691.352,1720.96 691.352,1720.96 691.634,1720.96 691.352,1720.96 "/>
<path clip-path="url(#clip322)" d="M691.634 1720.96 L691.634 1720.96 L691.916 1720.96 L691.916 1720.96 L691.634 1720.96 L691.634 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="691.634,1720.96 691.634,1720.96 691.916,1720.96 691.634,1720.96 "/>
<path clip-path="url(#clip322)" d="M691.916 1720.96 L691.916 1720.96 L692.198 1720.96 L692.198 1720.96 L691.916 1720.96 L691.916 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="691.916,1720.96 691.916,1720.96 692.198,1720.96 691.916,1720.96 "/>
<path clip-path="url(#clip322)" d="M692.198 1720.96 L692.198 1720.96 L692.479 1720.96 L692.479 1720.96 L692.198 1720.96 L692.198 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="692.198,1720.96 692.198,1720.96 692.479,1720.96 692.198,1720.96 "/>
<path clip-path="url(#clip322)" d="M692.479 1720.96 L692.479 1720.96 L692.761 1720.96 L692.761 1720.96 L692.479 1720.96 L692.479 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="692.479,1720.96 692.479,1720.96 692.761,1720.96 692.479,1720.96 "/>
<path clip-path="url(#clip322)" d="M692.761 1720.96 L692.761 1720.96 L693.043 1720.96 L693.043 1720.96 L692.761 1720.96 L692.761 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="692.761,1720.96 692.761,1720.96 693.043,1720.96 692.761,1720.96 "/>
<path clip-path="url(#clip322)" d="M693.043 1720.96 L693.043 1720.96 L693.325 1720.96 L693.325 1720.96 L693.043 1720.96 L693.043 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="693.043,1720.96 693.043,1720.96 693.325,1720.96 693.043,1720.96 "/>
<path clip-path="url(#clip322)" d="M693.325 1720.96 L693.325 1720.96 L693.606 1720.96 L693.606 1720.96 L693.325 1720.96 L693.325 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="693.325,1720.96 693.325,1720.96 693.606,1720.96 693.325,1720.96 "/>
<path clip-path="url(#clip322)" d="M693.606 1720.96 L693.606 1720.96 L693.888 1720.96 L693.888 1720.96 L693.606 1720.96 L693.606 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="693.606,1720.96 693.606,1720.96 693.888,1720.96 693.606,1720.96 "/>
<path clip-path="url(#clip322)" d="M693.888 1720.96 L693.888 1720.96 L694.17 1720.96 L694.17 1720.96 L693.888 1720.96 L693.888 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="693.888,1720.96 693.888,1720.96 694.17,1720.96 693.888,1720.96 "/>
<path clip-path="url(#clip322)" d="M694.17 1720.96 L694.17 1720.96 L694.451 1720.96 L694.451 1720.96 L694.17 1720.96 L694.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="694.17,1720.96 694.17,1720.96 694.451,1720.96 694.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M694.451 1720.96 L694.451 1720.96 L694.733 1720.96 L694.733 1720.96 L694.451 1720.96 L694.451 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="694.451,1720.96 694.451,1720.96 694.733,1720.96 694.451,1720.96 "/>
<path clip-path="url(#clip322)" d="M694.733 1720.96 L694.733 1720.96 L695.015 1720.96 L695.015 1720.96 L694.733 1720.96 L694.733 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="694.733,1720.96 694.733,1720.96 695.015,1720.96 694.733,1720.96 "/>
<path clip-path="url(#clip322)" d="M695.015 1720.96 L695.015 1720.96 L695.297 1720.96 L695.297 1720.96 L695.015 1720.96 L695.015 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="695.015,1720.96 695.015,1720.96 695.297,1720.96 695.015,1720.96 "/>
<path clip-path="url(#clip322)" d="M695.297 1720.96 L695.297 1720.96 L695.578 1720.96 L695.578 1720.96 L695.297 1720.96 L695.297 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="695.297,1720.96 695.297,1720.96 695.578,1720.96 695.297,1720.96 "/>
<path clip-path="url(#clip322)" d="M695.578 1720.96 L695.578 1720.96 L695.86 1720.96 L695.86 1720.96 L695.578 1720.96 L695.578 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="695.578,1720.96 695.578,1720.96 695.86,1720.96 695.578,1720.96 "/>
<path clip-path="url(#clip322)" d="M695.86 1720.96 L695.86 1720.96 L696.142 1720.96 L696.142 1720.96 L695.86 1720.96 L695.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="695.86,1720.96 695.86,1720.96 696.142,1720.96 695.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M696.142 1720.96 L696.142 1720.96 L696.424 1720.96 L696.424 1720.96 L696.142 1720.96 L696.142 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="696.142,1720.96 696.142,1720.96 696.424,1720.96 696.142,1720.96 "/>
<path clip-path="url(#clip322)" d="M696.424 1720.96 L696.424 1720.96 L696.705 1720.96 L696.705 1720.96 L696.424 1720.96 L696.424 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="696.424,1720.96 696.424,1720.96 696.705,1720.96 696.424,1720.96 "/>
<path clip-path="url(#clip322)" d="M696.705 1720.96 L696.705 1720.96 L696.987 1720.96 L696.987 1720.96 L696.705 1720.96 L696.705 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="696.705,1720.96 696.705,1720.96 696.987,1720.96 696.705,1720.96 "/>
<path clip-path="url(#clip322)" d="M696.987 1720.96 L696.987 1720.96 L697.269 1720.96 L697.269 1720.96 L696.987 1720.96 L696.987 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="696.987,1720.96 696.987,1720.96 697.269,1720.96 696.987,1720.96 "/>
<path clip-path="url(#clip322)" d="M697.269 1720.96 L697.269 1720.96 L697.55 1720.96 L697.55 1720.96 L697.269 1720.96 L697.269 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="697.269,1720.96 697.269,1720.96 697.55,1720.96 697.269,1720.96 "/>
<path clip-path="url(#clip322)" d="M697.55 1720.96 L697.55 1720.96 L697.832 1720.96 L697.832 1720.96 L697.55 1720.96 L697.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="697.55,1720.96 697.55,1720.96 697.832,1720.96 697.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M697.832 1720.96 L697.832 1720.96 L698.114 1720.96 L698.114 1720.96 L697.832 1720.96 L697.832 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="697.832,1720.96 697.832,1720.96 698.114,1720.96 697.832,1720.96 "/>
<path clip-path="url(#clip322)" d="M698.114 1720.96 L698.114 1720.96 L698.396 1720.96 L698.396 1720.96 L698.114 1720.96 L698.114 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="698.114,1720.96 698.114,1720.96 698.396,1720.96 698.114,1720.96 "/>
<path clip-path="url(#clip322)" d="M698.396 1720.96 L698.396 1720.96 L698.677 1720.96 L698.677 1720.96 L698.396 1720.96 L698.396 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="698.396,1720.96 698.396,1720.96 698.677,1720.96 698.396,1720.96 "/>
<path clip-path="url(#clip322)" d="M698.677 1720.96 L698.677 1720.96 L698.959 1720.96 L698.959 1720.96 L698.677 1720.96 L698.677 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="698.677,1720.96 698.677,1720.96 698.959,1720.96 698.677,1720.96 "/>
<path clip-path="url(#clip322)" d="M698.959 1720.96 L698.959 1720.96 L699.241 1720.96 L699.241 1720.96 L698.959 1720.96 L698.959 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="698.959,1720.96 698.959,1720.96 699.241,1720.96 698.959,1720.96 "/>
<path clip-path="url(#clip322)" d="M699.241 1720.96 L699.241 1720.96 L699.522 1720.96 L699.522 1720.96 L699.241 1720.96 L699.241 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="699.241,1720.96 699.241,1720.96 699.522,1720.96 699.241,1720.96 "/>
<path clip-path="url(#clip322)" d="M699.522 1720.96 L699.522 1720.96 L699.804 1720.96 L699.804 1720.96 L699.522 1720.96 L699.522 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="699.522,1720.96 699.522,1720.96 699.804,1720.96 699.522,1720.96 "/>
<path clip-path="url(#clip322)" d="M699.804 1720.96 L699.804 1720.96 L700.086 1720.96 L700.086 1720.96 L699.804 1720.96 L699.804 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="699.804,1720.96 699.804,1720.96 700.086,1720.96 699.804,1720.96 "/>
<path clip-path="url(#clip322)" d="M700.086 1720.96 L700.086 1720.96 L700.368 1720.96 L700.368 1720.96 L700.086 1720.96 L700.086 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="700.086,1720.96 700.086,1720.96 700.368,1720.96 700.086,1720.96 "/>
<path clip-path="url(#clip322)" d="M700.368 1720.96 L700.368 1720.96 L700.649 1720.96 L700.649 1720.96 L700.368 1720.96 L700.368 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="700.368,1720.96 700.368,1720.96 700.649,1720.96 700.368,1720.96 "/>
<path clip-path="url(#clip322)" d="M700.649 1720.96 L700.649 1720.96 L700.931 1720.96 L700.931 1720.96 L700.649 1720.96 L700.649 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="700.649,1720.96 700.649,1720.96 700.931,1720.96 700.649,1720.96 "/>
<path clip-path="url(#clip322)" d="M700.931 1720.96 L700.931 1720.96 L701.213 1720.96 L701.213 1720.96 L700.931 1720.96 L700.931 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="700.931,1720.96 700.931,1720.96 701.213,1720.96 700.931,1720.96 "/>
<path clip-path="url(#clip322)" d="M701.213 1720.96 L701.213 1720.96 L701.495 1720.96 L701.495 1720.96 L701.213 1720.96 L701.213 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="701.213,1720.96 701.213,1720.96 701.495,1720.96 701.213,1720.96 "/>
<path clip-path="url(#clip322)" d="M701.495 1720.96 L701.495 1720.96 L701.776 1720.96 L701.776 1720.96 L701.495 1720.96 L701.495 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="701.495,1720.96 701.495,1720.96 701.776,1720.96 701.495,1720.96 "/>
<path clip-path="url(#clip322)" d="M701.776 1720.96 L701.776 1720.96 L702.058 1720.96 L702.058 1720.96 L701.776 1720.96 L701.776 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="701.776,1720.96 701.776,1720.96 702.058,1720.96 701.776,1720.96 "/>
<path clip-path="url(#clip322)" d="M702.058 1720.96 L702.058 1720.96 L702.34 1720.96 L702.34 1720.96 L702.058 1720.96 L702.058 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="702.058,1720.96 702.058,1720.96 702.34,1720.96 702.058,1720.96 "/>
<path clip-path="url(#clip322)" d="M702.34 1720.96 L702.34 1720.96 L702.621 1720.96 L702.621 1720.96 L702.34 1720.96 L702.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="702.34,1720.96 702.34,1720.96 702.621,1720.96 702.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M702.621 1720.96 L702.621 1720.96 L702.903 1720.96 L702.903 1720.96 L702.621 1720.96 L702.621 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="702.621,1720.96 702.621,1720.96 702.903,1720.96 702.621,1720.96 "/>
<path clip-path="url(#clip322)" d="M702.903 1720.96 L702.903 1720.96 L703.185 1720.96 L703.185 1720.96 L702.903 1720.96 L702.903 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="702.903,1720.96 702.903,1720.96 703.185,1720.96 702.903,1720.96 "/>
<path clip-path="url(#clip322)" d="M703.185 1720.96 L703.185 1720.96 L703.467 1720.96 L703.467 1720.96 L703.185 1720.96 L703.185 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="703.185,1720.96 703.185,1720.96 703.467,1720.96 703.185,1720.96 "/>
<path clip-path="url(#clip322)" d="M703.467 1720.96 L703.467 1720.96 L703.748 1720.96 L703.748 1720.96 L703.467 1720.96 L703.467 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="703.467,1720.96 703.467,1720.96 703.748,1720.96 703.467,1720.96 "/>
<path clip-path="url(#clip322)" d="M703.748 1720.96 L703.748 1720.96 L704.03 1720.96 L704.03 1720.96 L703.748 1720.96 L703.748 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="703.748,1720.96 703.748,1720.96 704.03,1720.96 703.748,1720.96 "/>
<path clip-path="url(#clip322)" d="M704.03 1720.96 L704.03 1720.96 L704.312 1720.96 L704.312 1720.96 L704.03 1720.96 L704.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="704.03,1720.96 704.03,1720.96 704.312,1720.96 704.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M704.312 1720.96 L704.312 1720.96 L704.594 1720.96 L704.594 1720.96 L704.312 1720.96 L704.312 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="704.312,1720.96 704.312,1720.96 704.594,1720.96 704.312,1720.96 "/>
<path clip-path="url(#clip322)" d="M704.594 1720.96 L704.594 1720.96 L704.875 1720.96 L704.875 1720.96 L704.594 1720.96 L704.594 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="704.594,1720.96 704.594,1720.96 704.875,1720.96 704.594,1720.96 "/>
<path clip-path="url(#clip322)" d="M704.875 1720.96 L704.875 1720.96 L705.157 1720.96 L705.157 1720.96 L704.875 1720.96 L704.875 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="704.875,1720.96 704.875,1720.96 705.157,1720.96 704.875,1720.96 "/>
<path clip-path="url(#clip322)" d="M705.157 1720.96 L705.157 1720.96 L705.439 1720.96 L705.439 1720.96 L705.157 1720.96 L705.157 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="705.157,1720.96 705.157,1720.96 705.439,1720.96 705.157,1720.96 "/>
<path clip-path="url(#clip322)" d="M705.439 1720.96 L705.439 1720.96 L705.72 1720.96 L705.72 1720.96 L705.439 1720.96 L705.439 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="705.439,1720.96 705.439,1720.96 705.72,1720.96 705.439,1720.96 "/>
<path clip-path="url(#clip322)" d="M705.72 1720.96 L705.72 1720.96 L706.002 1720.96 L706.002 1720.96 L705.72 1720.96 L705.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="705.72,1720.96 705.72,1720.96 706.002,1720.96 705.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M706.002 1720.96 L706.002 1720.96 L706.284 1720.96 L706.284 1720.96 L706.002 1720.96 L706.002 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="706.002,1720.96 706.002,1720.96 706.284,1720.96 706.002,1720.96 "/>
<path clip-path="url(#clip322)" d="M706.284 1720.96 L706.284 1720.96 L706.566 1720.96 L706.566 1720.96 L706.284 1720.96 L706.284 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="706.284,1720.96 706.284,1720.96 706.566,1720.96 706.284,1720.96 "/>
<path clip-path="url(#clip322)" d="M706.566 1720.96 L706.566 1720.96 L706.847 1720.96 L706.847 1720.96 L706.566 1720.96 L706.566 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="706.566,1720.96 706.566,1720.96 706.847,1720.96 706.566,1720.96 "/>
<path clip-path="url(#clip322)" d="M706.847 1720.96 L706.847 1720.96 L707.129 1720.96 L707.129 1720.96 L706.847 1720.96 L706.847 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="706.847,1720.96 706.847,1720.96 707.129,1720.96 706.847,1720.96 "/>
<path clip-path="url(#clip322)" d="M707.129 1720.96 L707.129 1720.96 L707.411 1720.96 L707.411 1720.96 L707.129 1720.96 L707.129 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="707.129,1720.96 707.129,1720.96 707.411,1720.96 707.129,1720.96 "/>
<path clip-path="url(#clip322)" d="M707.411 1720.96 L707.411 1720.96 L707.693 1720.96 L707.693 1720.96 L707.411 1720.96 L707.411 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="707.411,1720.96 707.411,1720.96 707.693,1720.96 707.411,1720.96 "/>
<path clip-path="url(#clip322)" d="M707.693 1720.96 L707.693 1720.96 L707.974 1720.96 L707.974 1720.96 L707.693 1720.96 L707.693 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="707.693,1720.96 707.693,1720.96 707.974,1720.96 707.693,1720.96 "/>
<path clip-path="url(#clip322)" d="M707.974 1720.96 L707.974 1720.96 L708.256 1720.96 L708.256 1720.96 L707.974 1720.96 L707.974 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="707.974,1720.96 707.974,1720.96 708.256,1720.96 707.974,1720.96 "/>
<path clip-path="url(#clip322)" d="M708.256 1720.96 L708.256 1720.96 L708.538 1720.96 L708.538 1720.96 L708.256 1720.96 L708.256 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="708.256,1720.96 708.256,1720.96 708.538,1720.96 708.256,1720.96 "/>
<path clip-path="url(#clip322)" d="M708.538 1720.96 L708.538 1720.96 L708.819 1720.96 L708.819 1720.96 L708.538 1720.96 L708.538 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="708.538,1720.96 708.538,1720.96 708.819,1720.96 708.538,1720.96 "/>
<path clip-path="url(#clip322)" d="M708.819 1720.96 L708.819 1720.96 L709.101 1720.96 L709.101 1720.96 L708.819 1720.96 L708.819 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="708.819,1720.96 708.819,1720.96 709.101,1720.96 708.819,1720.96 "/>
<path clip-path="url(#clip322)" d="M709.101 1720.96 L709.101 1720.96 L709.383 1720.96 L709.383 1720.96 L709.101 1720.96 L709.101 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="709.101,1720.96 709.101,1720.96 709.383,1720.96 709.101,1720.96 "/>
<path clip-path="url(#clip322)" d="M709.383 1720.96 L709.383 1720.96 L709.665 1720.96 L709.665 1720.96 L709.383 1720.96 L709.383 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="709.383,1720.96 709.383,1720.96 709.665,1720.96 709.383,1720.96 "/>
<path clip-path="url(#clip322)" d="M709.665 1720.96 L709.665 1720.96 L709.946 1720.96 L709.946 1720.96 L709.665 1720.96 L709.665 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="709.665,1720.96 709.665,1720.96 709.946,1720.96 709.665,1720.96 "/>
<path clip-path="url(#clip322)" d="M709.946 1720.96 L709.946 1720.96 L710.228 1720.96 L710.228 1720.96 L709.946 1720.96 L709.946 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="709.946,1720.96 709.946,1720.96 710.228,1720.96 709.946,1720.96 "/>
<path clip-path="url(#clip322)" d="M710.228 1720.96 L710.228 1720.96 L710.51 1720.96 L710.51 1720.96 L710.228 1720.96 L710.228 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="710.228,1720.96 710.228,1720.96 710.51,1720.96 710.228,1720.96 "/>
<path clip-path="url(#clip322)" d="M710.51 1720.96 L710.51 1720.96 L710.792 1720.96 L710.792 1720.96 L710.51 1720.96 L710.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="710.51,1720.96 710.51,1720.96 710.792,1720.96 710.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M710.792 1720.96 L710.792 1720.96 L711.073 1720.96 L711.073 1720.96 L710.792 1720.96 L710.792 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="710.792,1720.96 710.792,1720.96 711.073,1720.96 710.792,1720.96 "/>
<path clip-path="url(#clip322)" d="M711.073 1720.96 L711.073 1720.96 L711.355 1720.96 L711.355 1720.96 L711.073 1720.96 L711.073 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="711.073,1720.96 711.073,1720.96 711.355,1720.96 711.073,1720.96 "/>
<path clip-path="url(#clip322)" d="M711.355 1720.96 L711.355 1720.96 L711.637 1720.96 L711.637 1720.96 L711.355 1720.96 L711.355 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="711.355,1720.96 711.355,1720.96 711.637,1720.96 711.355,1720.96 "/>
<path clip-path="url(#clip322)" d="M711.637 1720.96 L711.637 1720.96 L711.918 1720.96 L711.918 1720.96 L711.637 1720.96 L711.637 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="711.637,1720.96 711.637,1720.96 711.918,1720.96 711.637,1720.96 "/>
<path clip-path="url(#clip322)" d="M711.918 1720.96 L711.918 1720.96 L712.2 1720.96 L712.2 1720.96 L711.918 1720.96 L711.918 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="711.918,1720.96 711.918,1720.96 712.2,1720.96 711.918,1720.96 "/>
<path clip-path="url(#clip322)" d="M712.2 1720.96 L712.2 1720.96 L712.482 1720.96 L712.482 1720.96 L712.2 1720.96 L712.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="712.2,1720.96 712.2,1720.96 712.482,1720.96 712.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M712.482 1720.96 L712.482 1720.96 L712.764 1720.96 L712.764 1720.96 L712.482 1720.96 L712.482 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="712.482,1720.96 712.482,1720.96 712.764,1720.96 712.482,1720.96 "/>
<path clip-path="url(#clip322)" d="M712.764 1720.96 L712.764 1720.96 L713.045 1720.96 L713.045 1720.96 L712.764 1720.96 L712.764 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="712.764,1720.96 712.764,1720.96 713.045,1720.96 712.764,1720.96 "/>
<path clip-path="url(#clip322)" d="M713.045 1720.96 L713.045 1720.96 L713.327 1720.96 L713.327 1720.96 L713.045 1720.96 L713.045 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="713.045,1720.96 713.045,1720.96 713.327,1720.96 713.045,1720.96 "/>
<path clip-path="url(#clip322)" d="M713.327 1720.96 L713.327 1720.96 L713.609 1720.96 L713.609 1720.96 L713.327 1720.96 L713.327 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="713.327,1720.96 713.327,1720.96 713.609,1720.96 713.327,1720.96 "/>
<path clip-path="url(#clip322)" d="M713.609 1720.96 L713.609 1720.96 L713.89 1720.96 L713.89 1720.96 L713.609 1720.96 L713.609 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="713.609,1720.96 713.609,1720.96 713.89,1720.96 713.609,1720.96 "/>
<path clip-path="url(#clip322)" d="M713.89 1720.96 L713.89 1720.96 L714.172 1720.96 L714.172 1720.96 L713.89 1720.96 L713.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="713.89,1720.96 713.89,1720.96 714.172,1720.96 713.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M714.172 1720.96 L714.172 1720.96 L714.454 1720.96 L714.454 1720.96 L714.172 1720.96 L714.172 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="714.172,1720.96 714.172,1720.96 714.454,1720.96 714.172,1720.96 "/>
<path clip-path="url(#clip322)" d="M714.454 1720.96 L714.454 1720.96 L714.736 1720.96 L714.736 1720.96 L714.454 1720.96 L714.454 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="714.454,1720.96 714.454,1720.96 714.736,1720.96 714.454,1720.96 "/>
<path clip-path="url(#clip322)" d="M714.736 1720.96 L714.736 1720.96 L715.017 1720.96 L715.017 1720.96 L714.736 1720.96 L714.736 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="714.736,1720.96 714.736,1720.96 715.017,1720.96 714.736,1720.96 "/>
<path clip-path="url(#clip322)" d="M715.017 1720.96 L715.017 1720.96 L715.299 1720.96 L715.299 1720.96 L715.017 1720.96 L715.017 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="715.017,1720.96 715.017,1720.96 715.299,1720.96 715.017,1720.96 "/>
<path clip-path="url(#clip322)" d="M715.299 1720.96 L715.299 1720.96 L715.581 1720.96 L715.581 1720.96 L715.299 1720.96 L715.299 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="715.299,1720.96 715.299,1720.96 715.581,1720.96 715.299,1720.96 "/>
<path clip-path="url(#clip322)" d="M715.581 1720.96 L715.581 1720.96 L715.863 1720.96 L715.863 1720.96 L715.581 1720.96 L715.581 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="715.581,1720.96 715.581,1720.96 715.863,1720.96 715.581,1720.96 "/>
<path clip-path="url(#clip322)" d="M715.863 1720.96 L715.863 1720.96 L716.144 1720.96 L716.144 1720.96 L715.863 1720.96 L715.863 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="715.863,1720.96 715.863,1720.96 716.144,1720.96 715.863,1720.96 "/>
<path clip-path="url(#clip322)" d="M716.144 1720.96 L716.144 1720.96 L716.426 1720.96 L716.426 1720.96 L716.144 1720.96 L716.144 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="716.144,1720.96 716.144,1720.96 716.426,1720.96 716.144,1720.96 "/>
<path clip-path="url(#clip322)" d="M716.426 1720.96 L716.426 1720.96 L716.708 1720.96 L716.708 1720.96 L716.426 1720.96 L716.426 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="716.426,1720.96 716.426,1720.96 716.708,1720.96 716.426,1720.96 "/>
<path clip-path="url(#clip322)" d="M716.708 1720.96 L716.708 1720.96 L716.989 1720.96 L716.989 1720.96 L716.708 1720.96 L716.708 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="716.708,1720.96 716.708,1720.96 716.989,1720.96 716.708,1720.96 "/>
<path clip-path="url(#clip322)" d="M716.989 1720.96 L716.989 1720.96 L717.271 1720.96 L717.271 1720.96 L716.989 1720.96 L716.989 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="716.989,1720.96 716.989,1720.96 717.271,1720.96 716.989,1720.96 "/>
<path clip-path="url(#clip322)" d="M717.271 1720.96 L717.271 1720.96 L717.553 1720.96 L717.553 1720.96 L717.271 1720.96 L717.271 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="717.271,1720.96 717.271,1720.96 717.553,1720.96 717.271,1720.96 "/>
<path clip-path="url(#clip322)" d="M717.553 1720.96 L717.553 1720.96 L717.835 1720.96 L717.835 1720.96 L717.553 1720.96 L717.553 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="717.553,1720.96 717.553,1720.96 717.835,1720.96 717.553,1720.96 "/>
<path clip-path="url(#clip322)" d="M717.835 1720.96 L717.835 1720.96 L718.116 1720.96 L718.116 1720.96 L717.835 1720.96 L717.835 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="717.835,1720.96 717.835,1720.96 718.116,1720.96 717.835,1720.96 "/>
<path clip-path="url(#clip322)" d="M718.116 1720.96 L718.116 1720.96 L718.398 1720.96 L718.398 1720.96 L718.116 1720.96 L718.116 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="718.116,1720.96 718.116,1720.96 718.398,1720.96 718.116,1720.96 "/>
<path clip-path="url(#clip322)" d="M718.398 1720.96 L718.398 1720.96 L718.68 1720.96 L718.68 1720.96 L718.398 1720.96 L718.398 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="718.398,1720.96 718.398,1720.96 718.68,1720.96 718.398,1720.96 "/>
<path clip-path="url(#clip322)" d="M718.68 1720.96 L718.68 1720.96 L718.962 1720.96 L718.962 1720.96 L718.68 1720.96 L718.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="718.68,1720.96 718.68,1720.96 718.962,1720.96 718.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M718.962 1720.96 L718.962 1720.96 L719.243 1720.96 L719.243 1720.96 L718.962 1720.96 L718.962 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="718.962,1720.96 718.962,1720.96 719.243,1720.96 718.962,1720.96 "/>
<path clip-path="url(#clip322)" d="M719.243 1720.96 L719.243 1720.96 L719.525 1720.96 L719.525 1720.96 L719.243 1720.96 L719.243 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="719.243,1720.96 719.243,1720.96 719.525,1720.96 719.243,1720.96 "/>
<path clip-path="url(#clip322)" d="M719.525 1720.96 L719.525 1720.96 L719.807 1720.96 L719.807 1720.96 L719.525 1720.96 L719.525 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="719.525,1720.96 719.525,1720.96 719.807,1720.96 719.525,1720.96 "/>
<path clip-path="url(#clip322)" d="M719.807 1720.96 L719.807 1720.96 L720.088 1720.96 L720.088 1720.96 L719.807 1720.96 L719.807 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="719.807,1720.96 719.807,1720.96 720.088,1720.96 719.807,1720.96 "/>
<path clip-path="url(#clip322)" d="M720.088 1720.96 L720.088 1720.96 L720.37 1720.96 L720.37 1720.96 L720.088 1720.96 L720.088 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="720.088,1720.96 720.088,1720.96 720.37,1720.96 720.088,1720.96 "/>
<path clip-path="url(#clip322)" d="M720.37 1720.96 L720.37 1720.96 L720.652 1720.96 L720.652 1720.96 L720.37 1720.96 L720.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="720.37,1720.96 720.37,1720.96 720.652,1720.96 720.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M720.652 1720.96 L720.652 1720.96 L720.934 1720.96 L720.934 1720.96 L720.652 1720.96 L720.652 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="720.652,1720.96 720.652,1720.96 720.934,1720.96 720.652,1720.96 "/>
<path clip-path="url(#clip322)" d="M720.934 1720.96 L720.934 1720.96 L721.215 1720.96 L721.215 1720.96 L720.934 1720.96 L720.934 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="720.934,1720.96 720.934,1720.96 721.215,1720.96 720.934,1720.96 "/>
<path clip-path="url(#clip322)" d="M721.215 1720.96 L721.215 1720.96 L721.497 1720.96 L721.497 1720.96 L721.215 1720.96 L721.215 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="721.215,1720.96 721.215,1720.96 721.497,1720.96 721.215,1720.96 "/>
<path clip-path="url(#clip322)" d="M721.497 1720.96 L721.497 1720.96 L721.779 1720.96 L721.779 1720.96 L721.497 1720.96 L721.497 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="721.497,1720.96 721.497,1720.96 721.779,1720.96 721.497,1720.96 "/>
<path clip-path="url(#clip322)" d="M721.779 1720.96 L721.779 1720.96 L722.061 1720.96 L722.061 1720.96 L721.779 1720.96 L721.779 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="721.779,1720.96 721.779,1720.96 722.061,1720.96 721.779,1720.96 "/>
<path clip-path="url(#clip322)" d="M722.061 1720.96 L722.061 1720.96 L722.342 1720.96 L722.342 1720.96 L722.061 1720.96 L722.061 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="722.061,1720.96 722.061,1720.96 722.342,1720.96 722.061,1720.96 "/>
<path clip-path="url(#clip322)" d="M722.342 1720.96 L722.342 1720.96 L722.624 1720.96 L722.624 1720.96 L722.342 1720.96 L722.342 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="722.342,1720.96 722.342,1720.96 722.624,1720.96 722.342,1720.96 "/>
<path clip-path="url(#clip322)" d="M722.624 1720.96 L722.624 1720.96 L722.906 1720.96 L722.906 1720.96 L722.624 1720.96 L722.624 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="722.624,1720.96 722.624,1720.96 722.906,1720.96 722.624,1720.96 "/>
<path clip-path="url(#clip322)" d="M722.906 1720.96 L722.906 1720.96 L723.187 1720.96 L723.187 1720.96 L722.906 1720.96 L722.906 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="722.906,1720.96 722.906,1720.96 723.187,1720.96 722.906,1720.96 "/>
<path clip-path="url(#clip322)" d="M723.187 1720.96 L723.187 1720.96 L723.469 1720.96 L723.469 1720.96 L723.187 1720.96 L723.187 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="723.187,1720.96 723.187,1720.96 723.469,1720.96 723.187,1720.96 "/>
<path clip-path="url(#clip322)" d="M723.469 1720.96 L723.469 1720.96 L723.751 1720.96 L723.751 1720.96 L723.469 1720.96 L723.469 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="723.469,1720.96 723.469,1720.96 723.751,1720.96 723.469,1720.96 "/>
<path clip-path="url(#clip322)" d="M723.751 1720.96 L723.751 1720.96 L724.033 1720.96 L724.033 1720.96 L723.751 1720.96 L723.751 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="723.751,1720.96 723.751,1720.96 724.033,1720.96 723.751,1720.96 "/>
<path clip-path="url(#clip322)" d="M724.033 1720.96 L724.033 1720.96 L724.314 1720.96 L724.314 1720.96 L724.033 1720.96 L724.033 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="724.033,1720.96 724.033,1720.96 724.314,1720.96 724.033,1720.96 "/>
<path clip-path="url(#clip322)" d="M724.314 1720.96 L724.314 1720.96 L724.596 1720.96 L724.596 1720.96 L724.314 1720.96 L724.314 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="724.314,1720.96 724.314,1720.96 724.596,1720.96 724.314,1720.96 "/>
<path clip-path="url(#clip322)" d="M724.596 1720.96 L724.596 1720.96 L724.878 1720.96 L724.878 1720.96 L724.596 1720.96 L724.596 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="724.596,1720.96 724.596,1720.96 724.878,1720.96 724.596,1720.96 "/>
<path clip-path="url(#clip322)" d="M724.878 1720.96 L724.878 1720.96 L725.16 1720.96 L725.16 1720.96 L724.878 1720.96 L724.878 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="724.878,1720.96 724.878,1720.96 725.16,1720.96 724.878,1720.96 "/>
<path clip-path="url(#clip322)" d="M725.16 1720.96 L725.16 1720.96 L725.441 1720.96 L725.441 1720.96 L725.16 1720.96 L725.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="725.16,1720.96 725.16,1720.96 725.441,1720.96 725.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M725.441 1720.96 L725.441 1720.96 L725.723 1720.96 L725.723 1720.96 L725.441 1720.96 L725.441 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="725.441,1720.96 725.441,1720.96 725.723,1720.96 725.441,1720.96 "/>
<path clip-path="url(#clip322)" d="M725.723 1720.96 L725.723 1720.96 L726.005 1720.96 L726.005 1720.96 L725.723 1720.96 L725.723 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="725.723,1720.96 725.723,1720.96 726.005,1720.96 725.723,1720.96 "/>
<path clip-path="url(#clip322)" d="M726.005 1720.96 L726.005 1720.96 L726.286 1720.96 L726.286 1720.96 L726.005 1720.96 L726.005 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="726.005,1720.96 726.005,1720.96 726.286,1720.96 726.005,1720.96 "/>
<path clip-path="url(#clip322)" d="M726.286 1720.96 L726.286 1720.96 L726.568 1720.96 L726.568 1720.96 L726.286 1720.96 L726.286 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="726.286,1720.96 726.286,1720.96 726.568,1720.96 726.286,1720.96 "/>
<path clip-path="url(#clip322)" d="M726.568 1720.96 L726.568 1720.96 L726.85 1720.96 L726.85 1720.96 L726.568 1720.96 L726.568 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="726.568,1720.96 726.568,1720.96 726.85,1720.96 726.568,1720.96 "/>
<path clip-path="url(#clip322)" d="M726.85 1720.96 L726.85 1720.96 L727.132 1720.96 L727.132 1720.96 L726.85 1720.96 L726.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="726.85,1720.96 726.85,1720.96 727.132,1720.96 726.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M727.132 1720.96 L727.132 1720.96 L727.413 1720.96 L727.413 1720.96 L727.132 1720.96 L727.132 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="727.132,1720.96 727.132,1720.96 727.413,1720.96 727.132,1720.96 "/>
<path clip-path="url(#clip322)" d="M727.413 1720.96 L727.413 1720.96 L727.695 1720.96 L727.695 1720.96 L727.413 1720.96 L727.413 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="727.413,1720.96 727.413,1720.96 727.695,1720.96 727.413,1720.96 "/>
<path clip-path="url(#clip322)" d="M727.695 1720.96 L727.695 1720.96 L727.977 1720.96 L727.977 1720.96 L727.695 1720.96 L727.695 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="727.695,1720.96 727.695,1720.96 727.977,1720.96 727.695,1720.96 "/>
<path clip-path="url(#clip322)" d="M727.977 1720.96 L727.977 1720.96 L728.259 1720.96 L728.259 1720.96 L727.977 1720.96 L727.977 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="727.977,1720.96 727.977,1720.96 728.259,1720.96 727.977,1720.96 "/>
<path clip-path="url(#clip322)" d="M728.259 1720.96 L728.259 1720.96 L728.54 1720.96 L728.54 1720.96 L728.259 1720.96 L728.259 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="728.259,1720.96 728.259,1720.96 728.54,1720.96 728.259,1720.96 "/>
<path clip-path="url(#clip322)" d="M728.54 1720.96 L728.54 1720.96 L728.822 1720.96 L728.822 1720.96 L728.54 1720.96 L728.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="728.54,1720.96 728.54,1720.96 728.822,1720.96 728.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M728.822 1720.96 L728.822 1720.96 L729.104 1720.96 L729.104 1720.96 L728.822 1720.96 L728.822 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="728.822,1720.96 728.822,1720.96 729.104,1720.96 728.822,1720.96 "/>
<path clip-path="url(#clip322)" d="M729.104 1720.96 L729.104 1720.96 L729.385 1720.96 L729.385 1720.96 L729.104 1720.96 L729.104 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="729.104,1720.96 729.104,1720.96 729.385,1720.96 729.104,1720.96 "/>
<path clip-path="url(#clip322)" d="M729.385 1720.96 L729.385 1720.96 L729.667 1720.96 L729.667 1720.96 L729.385 1720.96 L729.385 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="729.385,1720.96 729.385,1720.96 729.667,1720.96 729.385,1720.96 "/>
<path clip-path="url(#clip322)" d="M729.667 1720.96 L729.667 1720.96 L729.949 1720.96 L729.949 1720.96 L729.667 1720.96 L729.667 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="729.667,1720.96 729.667,1720.96 729.949,1720.96 729.667,1720.96 "/>
<path clip-path="url(#clip322)" d="M729.949 1720.96 L729.949 1720.96 L730.231 1720.96 L730.231 1720.96 L729.949 1720.96 L729.949 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="729.949,1720.96 729.949,1720.96 730.231,1720.96 729.949,1720.96 "/>
<path clip-path="url(#clip322)" d="M730.231 1720.96 L730.231 1720.96 L730.512 1720.96 L730.512 1720.96 L730.231 1720.96 L730.231 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="730.231,1720.96 730.231,1720.96 730.512,1720.96 730.231,1720.96 "/>
<path clip-path="url(#clip322)" d="M730.512 1720.96 L730.512 1720.96 L730.794 1720.96 L730.794 1720.96 L730.512 1720.96 L730.512 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="730.512,1720.96 730.512,1720.96 730.794,1720.96 730.512,1720.96 "/>
<path clip-path="url(#clip322)" d="M730.794 1720.96 L730.794 1720.96 L731.076 1720.96 L731.076 1720.96 L730.794 1720.96 L730.794 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="730.794,1720.96 730.794,1720.96 731.076,1720.96 730.794,1720.96 "/>
<path clip-path="url(#clip322)" d="M731.076 1720.96 L731.076 1720.96 L731.357 1720.96 L731.357 1720.96 L731.076 1720.96 L731.076 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="731.076,1720.96 731.076,1720.96 731.357,1720.96 731.076,1720.96 "/>
<path clip-path="url(#clip322)" d="M731.357 1720.96 L731.357 1720.96 L731.639 1720.96 L731.639 1720.96 L731.357 1720.96 L731.357 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="731.357,1720.96 731.357,1720.96 731.639,1720.96 731.357,1720.96 "/>
<path clip-path="url(#clip322)" d="M731.639 1720.96 L731.639 1720.96 L731.921 1720.96 L731.921 1720.96 L731.639 1720.96 L731.639 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="731.639,1720.96 731.639,1720.96 731.921,1720.96 731.639,1720.96 "/>
<path clip-path="url(#clip322)" d="M731.921 1720.96 L731.921 1720.96 L732.203 1720.96 L732.203 1720.96 L731.921 1720.96 L731.921 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="731.921,1720.96 731.921,1720.96 732.203,1720.96 731.921,1720.96 "/>
<path clip-path="url(#clip322)" d="M732.203 1720.96 L732.203 1720.96 L732.484 1720.96 L732.484 1720.96 L732.203 1720.96 L732.203 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="732.203,1720.96 732.203,1720.96 732.484,1720.96 732.203,1720.96 "/>
<path clip-path="url(#clip322)" d="M732.484 1720.96 L732.484 1720.96 L732.766 1720.96 L732.766 1720.96 L732.484 1720.96 L732.484 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="732.484,1720.96 732.484,1720.96 732.766,1720.96 732.484,1720.96 "/>
<path clip-path="url(#clip322)" d="M732.766 1720.96 L732.766 1720.96 L733.048 1720.96 L733.048 1720.96 L732.766 1720.96 L732.766 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="732.766,1720.96 732.766,1720.96 733.048,1720.96 732.766,1720.96 "/>
<path clip-path="url(#clip322)" d="M733.048 1720.96 L733.048 1720.96 L733.33 1720.96 L733.33 1720.96 L733.048 1720.96 L733.048 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="733.048,1720.96 733.048,1720.96 733.33,1720.96 733.048,1720.96 "/>
<path clip-path="url(#clip322)" d="M733.33 1720.96 L733.33 1720.96 L733.611 1720.96 L733.611 1720.96 L733.33 1720.96 L733.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="733.33,1720.96 733.33,1720.96 733.611,1720.96 733.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M733.611 1720.96 L733.611 1720.96 L733.893 1720.96 L733.893 1720.96 L733.611 1720.96 L733.611 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="733.611,1720.96 733.611,1720.96 733.893,1720.96 733.611,1720.96 "/>
<path clip-path="url(#clip322)" d="M733.893 1720.96 L733.893 1720.96 L734.175 1720.96 L734.175 1720.96 L733.893 1720.96 L733.893 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="733.893,1720.96 733.893,1720.96 734.175,1720.96 733.893,1720.96 "/>
<path clip-path="url(#clip322)" d="M734.175 1720.96 L734.175 1720.96 L734.456 1720.96 L734.456 1720.96 L734.175 1720.96 L734.175 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="734.175,1720.96 734.175,1720.96 734.456,1720.96 734.175,1720.96 "/>
<path clip-path="url(#clip322)" d="M734.456 1720.96 L734.456 1720.96 L734.738 1720.96 L734.738 1720.96 L734.456 1720.96 L734.456 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="734.456,1720.96 734.456,1720.96 734.738,1720.96 734.456,1720.96 "/>
<path clip-path="url(#clip322)" d="M734.738 1720.96 L734.738 1720.96 L735.02 1720.96 L735.02 1720.96 L734.738 1720.96 L734.738 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="734.738,1720.96 734.738,1720.96 735.02,1720.96 734.738,1720.96 "/>
<path clip-path="url(#clip322)" d="M735.02 1720.96 L735.02 1720.96 L735.302 1720.96 L735.302 1720.96 L735.02 1720.96 L735.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="735.02,1720.96 735.02,1720.96 735.302,1720.96 735.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M735.302 1720.96 L735.302 1720.96 L735.583 1720.96 L735.583 1720.96 L735.302 1720.96 L735.302 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="735.302,1720.96 735.302,1720.96 735.583,1720.96 735.302,1720.96 "/>
<path clip-path="url(#clip322)" d="M735.583 1720.96 L735.583 1720.96 L735.865 1720.96 L735.865 1720.96 L735.583 1720.96 L735.583 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="735.583,1720.96 735.583,1720.96 735.865,1720.96 735.583,1720.96 "/>
<path clip-path="url(#clip322)" d="M735.865 1720.96 L735.865 1720.96 L736.147 1720.96 L736.147 1720.96 L735.865 1720.96 L735.865 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="735.865,1720.96 735.865,1720.96 736.147,1720.96 735.865,1720.96 "/>
<path clip-path="url(#clip322)" d="M736.147 1720.96 L736.147 1720.96 L736.429 1720.96 L736.429 1720.96 L736.147 1720.96 L736.147 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="736.147,1720.96 736.147,1720.96 736.429,1720.96 736.147,1720.96 "/>
<path clip-path="url(#clip322)" d="M736.429 1720.96 L736.429 1720.96 L736.71 1720.96 L736.71 1720.96 L736.429 1720.96 L736.429 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="736.429,1720.96 736.429,1720.96 736.71,1720.96 736.429,1720.96 "/>
<path clip-path="url(#clip322)" d="M736.71 1720.96 L736.71 1720.96 L736.992 1720.96 L736.992 1720.96 L736.71 1720.96 L736.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="736.71,1720.96 736.71,1720.96 736.992,1720.96 736.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M736.992 1720.96 L736.992 1720.96 L737.274 1720.96 L737.274 1720.96 L736.992 1720.96 L736.992 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="736.992,1720.96 736.992,1720.96 737.274,1720.96 736.992,1720.96 "/>
<path clip-path="url(#clip322)" d="M737.274 1720.96 L737.274 1720.96 L737.555 1720.96 L737.555 1720.96 L737.274 1720.96 L737.274 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="737.274,1720.96 737.274,1720.96 737.555,1720.96 737.274,1720.96 "/>
<path clip-path="url(#clip322)" d="M737.555 1720.96 L737.555 1720.96 L737.837 1720.96 L737.837 1720.96 L737.555 1720.96 L737.555 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="737.555,1720.96 737.555,1720.96 737.837,1720.96 737.555,1720.96 "/>
<path clip-path="url(#clip322)" d="M737.837 1720.96 L737.837 1720.96 L738.119 1720.96 L738.119 1720.96 L737.837 1720.96 L737.837 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="737.837,1720.96 737.837,1720.96 738.119,1720.96 737.837,1720.96 "/>
<path clip-path="url(#clip322)" d="M738.119 1720.96 L738.119 1720.96 L738.401 1720.96 L738.401 1720.96 L738.119 1720.96 L738.119 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="738.119,1720.96 738.119,1720.96 738.401,1720.96 738.119,1720.96 "/>
<path clip-path="url(#clip322)" d="M738.401 1720.96 L738.401 1720.96 L738.682 1720.96 L738.682 1720.96 L738.401 1720.96 L738.401 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="738.401,1720.96 738.401,1720.96 738.682,1720.96 738.401,1720.96 "/>
<path clip-path="url(#clip322)" d="M738.682 1720.96 L738.682 1720.96 L738.964 1720.96 L738.964 1720.96 L738.682 1720.96 L738.682 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="738.682,1720.96 738.682,1720.96 738.964,1720.96 738.682,1720.96 "/>
<path clip-path="url(#clip322)" d="M738.964 1720.96 L738.964 1720.96 L739.246 1720.96 L739.246 1720.96 L738.964 1720.96 L738.964 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="738.964,1720.96 738.964,1720.96 739.246,1720.96 738.964,1720.96 "/>
<path clip-path="url(#clip322)" d="M739.246 1720.96 L739.246 1720.96 L739.528 1720.96 L739.528 1720.96 L739.246 1720.96 L739.246 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="739.246,1720.96 739.246,1720.96 739.528,1720.96 739.246,1720.96 "/>
<path clip-path="url(#clip322)" d="M739.528 1720.96 L739.528 1720.96 L739.809 1720.96 L739.809 1720.96 L739.528 1720.96 L739.528 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="739.528,1720.96 739.528,1720.96 739.809,1720.96 739.528,1720.96 "/>
<path clip-path="url(#clip322)" d="M739.809 1720.96 L739.809 1720.96 L740.091 1720.96 L740.091 1720.96 L739.809 1720.96 L739.809 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="739.809,1720.96 739.809,1720.96 740.091,1720.96 739.809,1720.96 "/>
<path clip-path="url(#clip322)" d="M740.091 1720.96 L740.091 1720.96 L740.373 1720.96 L740.373 1720.96 L740.091 1720.96 L740.091 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="740.091,1720.96 740.091,1720.96 740.373,1720.96 740.091,1720.96 "/>
<path clip-path="url(#clip322)" d="M740.373 1720.96 L740.373 1720.96 L740.654 1720.96 L740.654 1720.96 L740.373 1720.96 L740.373 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="740.373,1720.96 740.373,1720.96 740.654,1720.96 740.373,1720.96 "/>
<path clip-path="url(#clip322)" d="M740.654 1720.96 L740.654 1720.96 L740.936 1720.96 L740.936 1720.96 L740.654 1720.96 L740.654 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="740.654,1720.96 740.654,1720.96 740.936,1720.96 740.654,1720.96 "/>
<path clip-path="url(#clip322)" d="M740.936 1720.96 L740.936 1720.96 L741.218 1720.96 L741.218 1720.96 L740.936 1720.96 L740.936 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="740.936,1720.96 740.936,1720.96 741.218,1720.96 740.936,1720.96 "/>
<path clip-path="url(#clip322)" d="M741.218 1720.96 L741.218 1720.96 L741.5 1720.96 L741.5 1720.96 L741.218 1720.96 L741.218 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="741.218,1720.96 741.218,1720.96 741.5,1720.96 741.218,1720.96 "/>
<path clip-path="url(#clip322)" d="M741.5 1720.96 L741.5 1720.96 L741.781 1720.96 L741.781 1720.96 L741.5 1720.96 L741.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="741.5,1720.96 741.5,1720.96 741.781,1720.96 741.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M741.781 1720.96 L741.781 1720.96 L742.063 1720.96 L742.063 1720.96 L741.781 1720.96 L741.781 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="741.781,1720.96 741.781,1720.96 742.063,1720.96 741.781,1720.96 "/>
<path clip-path="url(#clip322)" d="M742.063 1720.96 L742.063 1720.96 L742.345 1720.96 L742.345 1720.96 L742.063 1720.96 L742.063 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="742.063,1720.96 742.063,1720.96 742.345,1720.96 742.063,1720.96 "/>
<path clip-path="url(#clip322)" d="M742.345 1720.96 L742.345 1720.96 L742.627 1720.96 L742.627 1720.96 L742.345 1720.96 L742.345 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="742.345,1720.96 742.345,1720.96 742.627,1720.96 742.345,1720.96 "/>
<path clip-path="url(#clip322)" d="M742.627 1720.96 L742.627 1720.96 L742.908 1720.96 L742.908 1720.96 L742.627 1720.96 L742.627 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="742.627,1720.96 742.627,1720.96 742.908,1720.96 742.627,1720.96 "/>
<path clip-path="url(#clip322)" d="M742.908 1720.96 L742.908 1720.96 L743.19 1720.96 L743.19 1720.96 L742.908 1720.96 L742.908 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="742.908,1720.96 742.908,1720.96 743.19,1720.96 742.908,1720.96 "/>
<path clip-path="url(#clip322)" d="M743.19 1720.96 L743.19 1720.96 L743.472 1720.96 L743.472 1720.96 L743.19 1720.96 L743.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="743.19,1720.96 743.19,1720.96 743.472,1720.96 743.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M743.472 1720.96 L743.472 1720.96 L743.753 1720.96 L743.753 1720.96 L743.472 1720.96 L743.472 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="743.472,1720.96 743.472,1720.96 743.753,1720.96 743.472,1720.96 "/>
<path clip-path="url(#clip322)" d="M743.753 1720.96 L743.753 1720.96 L744.035 1720.96 L744.035 1720.96 L743.753 1720.96 L743.753 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="743.753,1720.96 743.753,1720.96 744.035,1720.96 743.753,1720.96 "/>
<path clip-path="url(#clip322)" d="M744.035 1720.96 L744.035 1720.96 L744.317 1720.96 L744.317 1720.96 L744.035 1720.96 L744.035 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="744.035,1720.96 744.035,1720.96 744.317,1720.96 744.035,1720.96 "/>
<path clip-path="url(#clip322)" d="M744.317 1720.96 L744.317 1720.96 L744.599 1720.96 L744.599 1720.96 L744.317 1720.96 L744.317 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="744.317,1720.96 744.317,1720.96 744.599,1720.96 744.317,1720.96 "/>
<path clip-path="url(#clip322)" d="M744.599 1720.96 L744.599 1720.96 L744.88 1720.96 L744.88 1720.96 L744.599 1720.96 L744.599 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="744.599,1720.96 744.599,1720.96 744.88,1720.96 744.599,1720.96 "/>
<path clip-path="url(#clip322)" d="M744.88 1720.96 L744.88 1720.96 L745.162 1720.96 L745.162 1720.96 L744.88 1720.96 L744.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="744.88,1720.96 744.88,1720.96 745.162,1720.96 744.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M745.162 1720.96 L745.162 1720.96 L745.444 1720.96 L745.444 1720.96 L745.162 1720.96 L745.162 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="745.162,1720.96 745.162,1720.96 745.444,1720.96 745.162,1720.96 "/>
<path clip-path="url(#clip322)" d="M745.444 1720.96 L745.444 1720.96 L745.725 1720.96 L745.725 1720.96 L745.444 1720.96 L745.444 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="745.444,1720.96 745.444,1720.96 745.725,1720.96 745.444,1720.96 "/>
<path clip-path="url(#clip322)" d="M745.725 1720.96 L745.725 1720.96 L746.007 1720.96 L746.007 1720.96 L745.725 1720.96 L745.725 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="745.725,1720.96 745.725,1720.96 746.007,1720.96 745.725,1720.96 "/>
<path clip-path="url(#clip322)" d="M746.007 1720.96 L746.007 1720.96 L746.289 1720.96 L746.289 1720.96 L746.007 1720.96 L746.007 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="746.007,1720.96 746.007,1720.96 746.289,1720.96 746.007,1720.96 "/>
<path clip-path="url(#clip322)" d="M746.289 1720.96 L746.289 1720.96 L746.571 1720.96 L746.571 1720.96 L746.289 1720.96 L746.289 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="746.289,1720.96 746.289,1720.96 746.571,1720.96 746.289,1720.96 "/>
<path clip-path="url(#clip322)" d="M746.571 1720.96 L746.571 1720.96 L746.852 1720.96 L746.852 1720.96 L746.571 1720.96 L746.571 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="746.571,1720.96 746.571,1720.96 746.852,1720.96 746.571,1720.96 "/>
<path clip-path="url(#clip322)" d="M746.852 1720.96 L746.852 1720.96 L747.134 1720.96 L747.134 1720.96 L746.852 1720.96 L746.852 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="746.852,1720.96 746.852,1720.96 747.134,1720.96 746.852,1720.96 "/>
<path clip-path="url(#clip322)" d="M747.134 1720.96 L747.134 1720.96 L747.416 1720.96 L747.416 1720.96 L747.134 1720.96 L747.134 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="747.134,1720.96 747.134,1720.96 747.416,1720.96 747.134,1720.96 "/>
<path clip-path="url(#clip322)" d="M747.416 1720.96 L747.416 1720.96 L747.698 1720.96 L747.698 1720.96 L747.416 1720.96 L747.416 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="747.416,1720.96 747.416,1720.96 747.698,1720.96 747.416,1720.96 "/>
<path clip-path="url(#clip322)" d="M747.698 1720.96 L747.698 1720.96 L747.979 1720.96 L747.979 1720.96 L747.698 1720.96 L747.698 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="747.698,1720.96 747.698,1720.96 747.979,1720.96 747.698,1720.96 "/>
<path clip-path="url(#clip322)" d="M747.979 1720.96 L747.979 1720.96 L748.261 1720.96 L748.261 1720.96 L747.979 1720.96 L747.979 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="747.979,1720.96 747.979,1720.96 748.261,1720.96 747.979,1720.96 "/>
<path clip-path="url(#clip322)" d="M748.261 1720.96 L748.261 1720.96 L748.543 1720.96 L748.543 1720.96 L748.261 1720.96 L748.261 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="748.261,1720.96 748.261,1720.96 748.543,1720.96 748.261,1720.96 "/>
<path clip-path="url(#clip322)" d="M748.543 1720.96 L748.543 1720.96 L748.824 1720.96 L748.824 1720.96 L748.543 1720.96 L748.543 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="748.543,1720.96 748.543,1720.96 748.824,1720.96 748.543,1720.96 "/>
<path clip-path="url(#clip322)" d="M748.824 1720.96 L748.824 1720.96 L749.106 1720.96 L749.106 1720.96 L748.824 1720.96 L748.824 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="748.824,1720.96 748.824,1720.96 749.106,1720.96 748.824,1720.96 "/>
<path clip-path="url(#clip322)" d="M749.106 1720.96 L749.106 1720.96 L749.388 1720.96 L749.388 1720.96 L749.106 1720.96 L749.106 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="749.106,1720.96 749.106,1720.96 749.388,1720.96 749.106,1720.96 "/>
<path clip-path="url(#clip322)" d="M749.388 1720.96 L749.388 1720.96 L749.67 1720.96 L749.67 1720.96 L749.388 1720.96 L749.388 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="749.388,1720.96 749.388,1720.96 749.67,1720.96 749.388,1720.96 "/>
<path clip-path="url(#clip322)" d="M749.67 1720.96 L749.67 1720.96 L749.951 1720.96 L749.951 1720.96 L749.67 1720.96 L749.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="749.67,1720.96 749.67,1720.96 749.951,1720.96 749.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M749.951 1720.96 L749.951 1720.96 L750.233 1720.96 L750.233 1720.96 L749.951 1720.96 L749.951 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="749.951,1720.96 749.951,1720.96 750.233,1720.96 749.951,1720.96 "/>
<path clip-path="url(#clip322)" d="M750.233 1720.96 L750.233 1720.96 L750.515 1720.96 L750.515 1720.96 L750.233 1720.96 L750.233 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="750.233,1720.96 750.233,1720.96 750.515,1720.96 750.233,1720.96 "/>
<path clip-path="url(#clip322)" d="M750.515 1720.96 L750.515 1720.96 L750.797 1720.96 L750.797 1720.96 L750.515 1720.96 L750.515 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="750.515,1720.96 750.515,1720.96 750.797,1720.96 750.515,1720.96 "/>
<path clip-path="url(#clip322)" d="M750.797 1720.96 L750.797 1720.96 L751.078 1720.96 L751.078 1720.96 L750.797 1720.96 L750.797 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="750.797,1720.96 750.797,1720.96 751.078,1720.96 750.797,1720.96 "/>
<path clip-path="url(#clip322)" d="M751.078 1720.96 L751.078 1720.96 L751.36 1720.96 L751.36 1720.96 L751.078 1720.96 L751.078 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="751.078,1720.96 751.078,1720.96 751.36,1720.96 751.078,1720.96 "/>
<path clip-path="url(#clip322)" d="M751.36 1720.96 L751.36 1720.96 L751.642 1720.96 L751.642 1720.96 L751.36 1720.96 L751.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="751.36,1720.96 751.36,1720.96 751.642,1720.96 751.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M751.642 1720.96 L751.642 1720.96 L751.923 1720.96 L751.923 1720.96 L751.642 1720.96 L751.642 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="751.642,1720.96 751.642,1720.96 751.923,1720.96 751.642,1720.96 "/>
<path clip-path="url(#clip322)" d="M751.923 1720.96 L751.923 1720.96 L752.205 1720.96 L752.205 1720.96 L751.923 1720.96 L751.923 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="751.923,1720.96 751.923,1720.96 752.205,1720.96 751.923,1720.96 "/>
<path clip-path="url(#clip322)" d="M752.205 1720.96 L752.205 1720.96 L752.487 1720.96 L752.487 1720.96 L752.205 1720.96 L752.205 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="752.205,1720.96 752.205,1720.96 752.487,1720.96 752.205,1720.96 "/>
<path clip-path="url(#clip322)" d="M752.487 1720.96 L752.487 1720.96 L752.769 1720.96 L752.769 1720.96 L752.487 1720.96 L752.487 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="752.487,1720.96 752.487,1720.96 752.769,1720.96 752.487,1720.96 "/>
<path clip-path="url(#clip322)" d="M752.769 1720.96 L752.769 1720.96 L753.05 1720.96 L753.05 1720.96 L752.769 1720.96 L752.769 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="752.769,1720.96 752.769,1720.96 753.05,1720.96 752.769,1720.96 "/>
<path clip-path="url(#clip322)" d="M753.05 1720.96 L753.05 1720.96 L753.332 1720.96 L753.332 1720.96 L753.05 1720.96 L753.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="753.05,1720.96 753.05,1720.96 753.332,1720.96 753.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M753.332 1720.96 L753.332 1720.96 L753.614 1720.96 L753.614 1720.96 L753.332 1720.96 L753.332 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="753.332,1720.96 753.332,1720.96 753.614,1720.96 753.332,1720.96 "/>
<path clip-path="url(#clip322)" d="M753.614 1720.96 L753.614 1720.96 L753.896 1720.96 L753.896 1720.96 L753.614 1720.96 L753.614 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="753.614,1720.96 753.614,1720.96 753.896,1720.96 753.614,1720.96 "/>
<path clip-path="url(#clip322)" d="M753.896 1720.96 L753.896 1720.96 L754.177 1720.96 L754.177 1720.96 L753.896 1720.96 L753.896 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="753.896,1720.96 753.896,1720.96 754.177,1720.96 753.896,1720.96 "/>
<path clip-path="url(#clip322)" d="M754.177 1720.96 L754.177 1720.96 L754.459 1720.96 L754.459 1720.96 L754.177 1720.96 L754.177 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="754.177,1720.96 754.177,1720.96 754.459,1720.96 754.177,1720.96 "/>
<path clip-path="url(#clip322)" d="M754.459 1720.96 L754.459 1720.96 L754.741 1720.96 L754.741 1720.96 L754.459 1720.96 L754.459 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="754.459,1720.96 754.459,1720.96 754.741,1720.96 754.459,1720.96 "/>
<path clip-path="url(#clip322)" d="M754.741 1720.96 L754.741 1720.96 L755.022 1720.96 L755.022 1720.96 L754.741 1720.96 L754.741 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="754.741,1720.96 754.741,1720.96 755.022,1720.96 754.741,1720.96 "/>
<path clip-path="url(#clip322)" d="M755.022 1720.96 L755.022 1720.96 L755.304 1720.96 L755.304 1720.96 L755.022 1720.96 L755.022 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="755.022,1720.96 755.022,1720.96 755.304,1720.96 755.022,1720.96 "/>
<path clip-path="url(#clip322)" d="M755.304 1720.96 L755.304 1720.96 L755.586 1720.96 L755.586 1720.96 L755.304 1720.96 L755.304 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="755.304,1720.96 755.304,1720.96 755.586,1720.96 755.304,1720.96 "/>
<path clip-path="url(#clip322)" d="M755.586 1720.96 L755.586 1720.96 L755.868 1720.96 L755.868 1720.96 L755.586 1720.96 L755.586 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="755.586,1720.96 755.586,1720.96 755.868,1720.96 755.586,1720.96 "/>
<path clip-path="url(#clip322)" d="M755.868 1720.96 L755.868 1720.96 L756.149 1720.96 L756.149 1720.96 L755.868 1720.96 L755.868 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="755.868,1720.96 755.868,1720.96 756.149,1720.96 755.868,1720.96 "/>
<path clip-path="url(#clip322)" d="M756.149 1720.96 L756.149 1720.96 L756.431 1720.96 L756.431 1720.96 L756.149 1720.96 L756.149 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="756.149,1720.96 756.149,1720.96 756.431,1720.96 756.149,1720.96 "/>
<path clip-path="url(#clip322)" d="M756.431 1720.96 L756.431 1720.96 L756.713 1720.96 L756.713 1720.96 L756.431 1720.96 L756.431 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="756.431,1720.96 756.431,1720.96 756.713,1720.96 756.431,1720.96 "/>
<path clip-path="url(#clip322)" d="M756.713 1720.96 L756.713 1720.96 L756.995 1720.96 L756.995 1720.96 L756.713 1720.96 L756.713 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="756.713,1720.96 756.713,1720.96 756.995,1720.96 756.713,1720.96 "/>
<path clip-path="url(#clip322)" d="M756.995 1720.96 L756.995 1720.96 L757.276 1720.96 L757.276 1720.96 L756.995 1720.96 L756.995 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="756.995,1720.96 756.995,1720.96 757.276,1720.96 756.995,1720.96 "/>
<path clip-path="url(#clip322)" d="M757.276 1720.96 L757.276 1720.96 L757.558 1720.96 L757.558 1720.96 L757.276 1720.96 L757.276 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="757.276,1720.96 757.276,1720.96 757.558,1720.96 757.276,1720.96 "/>
<path clip-path="url(#clip322)" d="M757.558 1720.96 L757.558 1720.96 L757.84 1720.96 L757.84 1720.96 L757.558 1720.96 L757.558 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="757.558,1720.96 757.558,1720.96 757.84,1720.96 757.558,1720.96 "/>
<path clip-path="url(#clip322)" d="M757.84 1720.96 L757.84 1720.96 L758.121 1720.96 L758.121 1720.96 L757.84 1720.96 L757.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="757.84,1720.96 757.84,1720.96 758.121,1720.96 757.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M758.121 1720.96 L758.121 1720.96 L758.403 1720.96 L758.403 1720.96 L758.121 1720.96 L758.121 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="758.121,1720.96 758.121,1720.96 758.403,1720.96 758.121,1720.96 "/>
<path clip-path="url(#clip322)" d="M758.403 1720.96 L758.403 1720.96 L758.685 1720.96 L758.685 1720.96 L758.403 1720.96 L758.403 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="758.403,1720.96 758.403,1720.96 758.685,1720.96 758.403,1720.96 "/>
<path clip-path="url(#clip322)" d="M758.685 1720.96 L758.685 1720.96 L758.967 1720.96 L758.967 1720.96 L758.685 1720.96 L758.685 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="758.685,1720.96 758.685,1720.96 758.967,1720.96 758.685,1720.96 "/>
<path clip-path="url(#clip322)" d="M758.967 1720.96 L758.967 1720.96 L759.248 1720.96 L759.248 1720.96 L758.967 1720.96 L758.967 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="758.967,1720.96 758.967,1720.96 759.248,1720.96 758.967,1720.96 "/>
<path clip-path="url(#clip322)" d="M759.248 1720.96 L759.248 1720.96 L759.53 1720.96 L759.53 1720.96 L759.248 1720.96 L759.248 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="759.248,1720.96 759.248,1720.96 759.53,1720.96 759.248,1720.96 "/>
<path clip-path="url(#clip322)" d="M759.53 1720.96 L759.53 1720.96 L759.812 1720.96 L759.812 1720.96 L759.53 1720.96 L759.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="759.53,1720.96 759.53,1720.96 759.812,1720.96 759.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M759.812 1720.96 L759.812 1720.96 L760.093 1720.96 L760.093 1720.96 L759.812 1720.96 L759.812 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="759.812,1720.96 759.812,1720.96 760.093,1720.96 759.812,1720.96 "/>
<path clip-path="url(#clip322)" d="M760.093 1720.96 L760.093 1720.96 L760.375 1720.96 L760.375 1720.96 L760.093 1720.96 L760.093 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="760.093,1720.96 760.093,1720.96 760.375,1720.96 760.093,1720.96 "/>
<path clip-path="url(#clip322)" d="M760.375 1720.96 L760.375 1720.96 L760.657 1720.96 L760.657 1720.96 L760.375 1720.96 L760.375 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="760.375,1720.96 760.375,1720.96 760.657,1720.96 760.375,1720.96 "/>
<path clip-path="url(#clip322)" d="M760.657 1720.96 L760.657 1720.96 L760.939 1720.96 L760.939 1720.96 L760.657 1720.96 L760.657 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="760.657,1720.96 760.657,1720.96 760.939,1720.96 760.657,1720.96 "/>
<path clip-path="url(#clip322)" d="M760.939 1720.96 L760.939 1720.96 L761.22 1720.96 L761.22 1720.96 L760.939 1720.96 L760.939 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="760.939,1720.96 760.939,1720.96 761.22,1720.96 760.939,1720.96 "/>
<path clip-path="url(#clip322)" d="M761.22 1720.96 L761.22 1720.96 L761.502 1720.96 L761.502 1720.96 L761.22 1720.96 L761.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="761.22,1720.96 761.22,1720.96 761.502,1720.96 761.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M761.502 1720.96 L761.502 1720.96 L761.784 1720.96 L761.784 1720.96 L761.502 1720.96 L761.502 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="761.502,1720.96 761.502,1720.96 761.784,1720.96 761.502,1720.96 "/>
<path clip-path="url(#clip322)" d="M761.784 1720.96 L761.784 1720.96 L762.066 1720.96 L762.066 1720.96 L761.784 1720.96 L761.784 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="761.784,1720.96 761.784,1720.96 762.066,1720.96 761.784,1720.96 "/>
<path clip-path="url(#clip322)" d="M762.066 1720.96 L762.066 1720.96 L762.347 1720.96 L762.347 1720.96 L762.066 1720.96 L762.066 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="762.066,1720.96 762.066,1720.96 762.347,1720.96 762.066,1720.96 "/>
<path clip-path="url(#clip322)" d="M762.347 1720.96 L762.347 1720.96 L762.629 1720.96 L762.629 1720.96 L762.347 1720.96 L762.347 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="762.347,1720.96 762.347,1720.96 762.629,1720.96 762.347,1720.96 "/>
<path clip-path="url(#clip322)" d="M762.629 1720.96 L762.629 1720.96 L762.911 1720.96 L762.911 1720.96 L762.629 1720.96 L762.629 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="762.629,1720.96 762.629,1720.96 762.911,1720.96 762.629,1720.96 "/>
<path clip-path="url(#clip322)" d="M762.911 1720.96 L762.911 1720.96 L763.192 1720.96 L763.192 1720.96 L762.911 1720.96 L762.911 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="762.911,1720.96 762.911,1720.96 763.192,1720.96 762.911,1720.96 "/>
<path clip-path="url(#clip322)" d="M763.192 1720.96 L763.192 1720.96 L763.474 1720.96 L763.474 1720.96 L763.192 1720.96 L763.192 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="763.192,1720.96 763.192,1720.96 763.474,1720.96 763.192,1720.96 "/>
<path clip-path="url(#clip322)" d="M763.474 1720.96 L763.474 1720.96 L763.756 1720.96 L763.756 1720.96 L763.474 1720.96 L763.474 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="763.474,1720.96 763.474,1720.96 763.756,1720.96 763.474,1720.96 "/>
<path clip-path="url(#clip322)" d="M763.756 1720.96 L763.756 1720.96 L764.038 1720.96 L764.038 1720.96 L763.756 1720.96 L763.756 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="763.756,1720.96 763.756,1720.96 764.038,1720.96 763.756,1720.96 "/>
<path clip-path="url(#clip322)" d="M764.038 1720.96 L764.038 1720.96 L764.319 1720.96 L764.319 1720.96 L764.038 1720.96 L764.038 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="764.038,1720.96 764.038,1720.96 764.319,1720.96 764.038,1720.96 "/>
<path clip-path="url(#clip322)" d="M764.319 1720.96 L764.319 1720.96 L764.601 1720.96 L764.601 1720.96 L764.319 1720.96 L764.319 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="764.319,1720.96 764.319,1720.96 764.601,1720.96 764.319,1720.96 "/>
<path clip-path="url(#clip322)" d="M764.601 1720.96 L764.601 1720.96 L764.883 1720.96 L764.883 1720.96 L764.601 1720.96 L764.601 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="764.601,1720.96 764.601,1720.96 764.883,1720.96 764.601,1720.96 "/>
<path clip-path="url(#clip322)" d="M764.883 1720.96 L764.883 1720.96 L765.165 1720.96 L765.165 1720.96 L764.883 1720.96 L764.883 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="764.883,1720.96 764.883,1720.96 765.165,1720.96 764.883,1720.96 "/>
<path clip-path="url(#clip322)" d="M765.165 1720.96 L765.165 1720.96 L765.446 1720.96 L765.446 1720.96 L765.165 1720.96 L765.165 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="765.165,1720.96 765.165,1720.96 765.446,1720.96 765.165,1720.96 "/>
<path clip-path="url(#clip322)" d="M765.446 1720.96 L765.446 1720.96 L765.728 1720.96 L765.728 1720.96 L765.446 1720.96 L765.446 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="765.446,1720.96 765.446,1720.96 765.728,1720.96 765.446,1720.96 "/>
<path clip-path="url(#clip322)" d="M765.728 1720.96 L765.728 1720.96 L766.01 1720.96 L766.01 1720.96 L765.728 1720.96 L765.728 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="765.728,1720.96 765.728,1720.96 766.01,1720.96 765.728,1720.96 "/>
<path clip-path="url(#clip322)" d="M766.01 1720.96 L766.01 1720.96 L766.291 1720.96 L766.291 1720.96 L766.01 1720.96 L766.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="766.01,1720.96 766.01,1720.96 766.291,1720.96 766.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M766.291 1720.96 L766.291 1720.96 L766.573 1720.96 L766.573 1720.96 L766.291 1720.96 L766.291 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="766.291,1720.96 766.291,1720.96 766.573,1720.96 766.291,1720.96 "/>
<path clip-path="url(#clip322)" d="M766.573 1720.96 L766.573 1720.96 L766.855 1720.96 L766.855 1720.96 L766.573 1720.96 L766.573 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="766.573,1720.96 766.573,1720.96 766.855,1720.96 766.573,1720.96 "/>
<path clip-path="url(#clip322)" d="M766.855 1720.96 L766.855 1720.96 L767.137 1720.96 L767.137 1720.96 L766.855 1720.96 L766.855 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="766.855,1720.96 766.855,1720.96 767.137,1720.96 766.855,1720.96 "/>
<path clip-path="url(#clip322)" d="M767.137 1720.96 L767.137 1720.96 L767.418 1720.96 L767.418 1720.96 L767.137 1720.96 L767.137 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="767.137,1720.96 767.137,1720.96 767.418,1720.96 767.137,1720.96 "/>
<path clip-path="url(#clip322)" d="M767.418 1720.96 L767.418 1720.96 L767.7 1720.96 L767.7 1720.96 L767.418 1720.96 L767.418 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="767.418,1720.96 767.418,1720.96 767.7,1720.96 767.418,1720.96 "/>
<path clip-path="url(#clip322)" d="M767.7 1720.96 L767.7 1720.96 L767.982 1720.96 L767.982 1720.96 L767.7 1720.96 L767.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="767.7,1720.96 767.7,1720.96 767.982,1720.96 767.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M767.982 1720.96 L767.982 1720.96 L768.264 1720.96 L768.264 1720.96 L767.982 1720.96 L767.982 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="767.982,1720.96 767.982,1720.96 768.264,1720.96 767.982,1720.96 "/>
<path clip-path="url(#clip322)" d="M768.264 1720.96 L768.264 1720.96 L768.545 1720.96 L768.545 1720.96 L768.264 1720.96 L768.264 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="768.264,1720.96 768.264,1720.96 768.545,1720.96 768.264,1720.96 "/>
<path clip-path="url(#clip322)" d="M768.545 1720.96 L768.545 1720.96 L768.827 1720.96 L768.827 1720.96 L768.545 1720.96 L768.545 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="768.545,1720.96 768.545,1720.96 768.827,1720.96 768.545,1720.96 "/>
<path clip-path="url(#clip322)" d="M768.827 1720.96 L768.827 1720.96 L769.109 1720.96 L769.109 1720.96 L768.827 1720.96 L768.827 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="768.827,1720.96 768.827,1720.96 769.109,1720.96 768.827,1720.96 "/>
<path clip-path="url(#clip322)" d="M769.109 1720.96 L769.109 1720.96 L769.39 1720.96 L769.39 1720.96 L769.109 1720.96 L769.109 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="769.109,1720.96 769.109,1720.96 769.39,1720.96 769.109,1720.96 "/>
<path clip-path="url(#clip322)" d="M769.39 1720.96 L769.39 1720.96 L769.672 1720.96 L769.672 1720.96 L769.39 1720.96 L769.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="769.39,1720.96 769.39,1720.96 769.672,1720.96 769.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M769.672 1720.96 L769.672 1720.96 L769.954 1720.96 L769.954 1720.96 L769.672 1720.96 L769.672 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="769.672,1720.96 769.672,1720.96 769.954,1720.96 769.672,1720.96 "/>
<path clip-path="url(#clip322)" d="M769.954 1720.96 L769.954 1720.96 L770.236 1720.96 L770.236 1720.96 L769.954 1720.96 L769.954 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="769.954,1720.96 769.954,1720.96 770.236,1720.96 769.954,1720.96 "/>
<path clip-path="url(#clip322)" d="M770.236 1720.96 L770.236 1720.96 L770.517 1720.96 L770.517 1720.96 L770.236 1720.96 L770.236 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="770.236,1720.96 770.236,1720.96 770.517,1720.96 770.236,1720.96 "/>
<path clip-path="url(#clip322)" d="M770.517 1720.96 L770.517 1720.96 L770.799 1720.96 L770.799 1720.96 L770.517 1720.96 L770.517 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="770.517,1720.96 770.517,1720.96 770.799,1720.96 770.517,1720.96 "/>
<path clip-path="url(#clip322)" d="M770.799 1720.96 L770.799 1720.96 L771.081 1720.96 L771.081 1720.96 L770.799 1720.96 L770.799 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="770.799,1720.96 770.799,1720.96 771.081,1720.96 770.799,1720.96 "/>
<path clip-path="url(#clip322)" d="M771.081 1720.96 L771.081 1720.96 L771.363 1720.96 L771.363 1720.96 L771.081 1720.96 L771.081 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="771.081,1720.96 771.081,1720.96 771.363,1720.96 771.081,1720.96 "/>
<path clip-path="url(#clip322)" d="M771.363 1720.96 L771.363 1720.96 L771.644 1720.96 L771.644 1720.96 L771.363 1720.96 L771.363 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="771.363,1720.96 771.363,1720.96 771.644,1720.96 771.363,1720.96 "/>
<path clip-path="url(#clip322)" d="M771.644 1720.96 L771.644 1720.96 L771.926 1720.96 L771.926 1720.96 L771.644 1720.96 L771.644 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="771.644,1720.96 771.644,1720.96 771.926,1720.96 771.644,1720.96 "/>
<path clip-path="url(#clip322)" d="M771.926 1720.96 L771.926 1720.96 L772.208 1720.96 L772.208 1720.96 L771.926 1720.96 L771.926 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="771.926,1720.96 771.926,1720.96 772.208,1720.96 771.926,1720.96 "/>
<path clip-path="url(#clip322)" d="M772.208 1720.96 L772.208 1720.96 L772.489 1720.96 L772.489 1720.96 L772.208 1720.96 L772.208 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="772.208,1720.96 772.208,1720.96 772.489,1720.96 772.208,1720.96 "/>
<path clip-path="url(#clip322)" d="M772.489 1720.96 L772.489 1720.96 L772.771 1720.96 L772.771 1720.96 L772.489 1720.96 L772.489 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="772.489,1720.96 772.489,1720.96 772.771,1720.96 772.489,1720.96 "/>
<path clip-path="url(#clip322)" d="M772.771 1720.96 L772.771 1720.96 L773.053 1720.96 L773.053 1720.96 L772.771 1720.96 L772.771 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="772.771,1720.96 772.771,1720.96 773.053,1720.96 772.771,1720.96 "/>
<path clip-path="url(#clip322)" d="M773.053 1720.96 L773.053 1720.96 L773.335 1720.96 L773.335 1720.96 L773.053 1720.96 L773.053 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="773.053,1720.96 773.053,1720.96 773.335,1720.96 773.053,1720.96 "/>
<path clip-path="url(#clip322)" d="M773.335 1720.96 L773.335 1720.96 L773.616 1720.96 L773.616 1720.96 L773.335 1720.96 L773.335 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="773.335,1720.96 773.335,1720.96 773.616,1720.96 773.335,1720.96 "/>
<path clip-path="url(#clip322)" d="M773.616 1720.96 L773.616 1720.96 L773.898 1720.96 L773.898 1720.96 L773.616 1720.96 L773.616 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="773.616,1720.96 773.616,1720.96 773.898,1720.96 773.616,1720.96 "/>
<path clip-path="url(#clip322)" d="M773.898 1720.96 L773.898 1720.96 L774.18 1720.96 L774.18 1720.96 L773.898 1720.96 L773.898 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="773.898,1720.96 773.898,1720.96 774.18,1720.96 773.898,1720.96 "/>
<path clip-path="url(#clip322)" d="M774.18 1720.96 L774.18 1720.96 L774.462 1720.96 L774.462 1720.96 L774.18 1720.96 L774.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="774.18,1720.96 774.18,1720.96 774.462,1720.96 774.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M774.462 1720.96 L774.462 1720.96 L774.743 1720.96 L774.743 1720.96 L774.462 1720.96 L774.462 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="774.462,1720.96 774.462,1720.96 774.743,1720.96 774.462,1720.96 "/>
<path clip-path="url(#clip322)" d="M774.743 1720.96 L774.743 1720.96 L775.025 1720.96 L775.025 1720.96 L774.743 1720.96 L774.743 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="774.743,1720.96 774.743,1720.96 775.025,1720.96 774.743,1720.96 "/>
<path clip-path="url(#clip322)" d="M775.025 1720.96 L775.025 1720.96 L775.307 1720.96 L775.307 1720.96 L775.025 1720.96 L775.025 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="775.025,1720.96 775.025,1720.96 775.307,1720.96 775.025,1720.96 "/>
<path clip-path="url(#clip322)" d="M775.307 1720.96 L775.307 1720.96 L775.588 1720.96 L775.588 1720.96 L775.307 1720.96 L775.307 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="775.307,1720.96 775.307,1720.96 775.588,1720.96 775.307,1720.96 "/>
<path clip-path="url(#clip322)" d="M775.588 1720.96 L775.588 1720.96 L775.87 1720.96 L775.87 1720.96 L775.588 1720.96 L775.588 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="775.588,1720.96 775.588,1720.96 775.87,1720.96 775.588,1720.96 "/>
<path clip-path="url(#clip322)" d="M775.87 1720.96 L775.87 1720.96 L776.152 1720.96 L776.152 1720.96 L775.87 1720.96 L775.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="775.87,1720.96 775.87,1720.96 776.152,1720.96 775.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M776.152 1720.96 L776.152 1720.96 L776.434 1720.96 L776.434 1720.96 L776.152 1720.96 L776.152 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="776.152,1720.96 776.152,1720.96 776.434,1720.96 776.152,1720.96 "/>
<path clip-path="url(#clip322)" d="M776.434 1720.96 L776.434 1720.96 L776.715 1720.96 L776.715 1720.96 L776.434 1720.96 L776.434 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="776.434,1720.96 776.434,1720.96 776.715,1720.96 776.434,1720.96 "/>
<path clip-path="url(#clip322)" d="M776.715 1720.96 L776.715 1720.96 L776.997 1720.96 L776.997 1720.96 L776.715 1720.96 L776.715 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="776.715,1720.96 776.715,1720.96 776.997,1720.96 776.715,1720.96 "/>
<path clip-path="url(#clip322)" d="M776.997 1720.96 L776.997 1720.96 L777.279 1720.96 L777.279 1720.96 L776.997 1720.96 L776.997 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="776.997,1720.96 776.997,1720.96 777.279,1720.96 776.997,1720.96 "/>
<path clip-path="url(#clip322)" d="M777.279 1720.96 L777.279 1720.96 L777.56 1720.96 L777.56 1720.96 L777.279 1720.96 L777.279 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="777.279,1720.96 777.279,1720.96 777.56,1720.96 777.279,1720.96 "/>
<path clip-path="url(#clip322)" d="M777.56 1720.96 L777.56 1720.96 L777.842 1720.96 L777.842 1720.96 L777.56 1720.96 L777.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="777.56,1720.96 777.56,1720.96 777.842,1720.96 777.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M777.842 1720.96 L777.842 1720.96 L778.124 1720.96 L778.124 1720.96 L777.842 1720.96 L777.842 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="777.842,1720.96 777.842,1720.96 778.124,1720.96 777.842,1720.96 "/>
<path clip-path="url(#clip322)" d="M778.124 1720.96 L778.124 1720.96 L778.406 1720.96 L778.406 1720.96 L778.124 1720.96 L778.124 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="778.124,1720.96 778.124,1720.96 778.406,1720.96 778.124,1720.96 "/>
<path clip-path="url(#clip322)" d="M778.406 1720.96 L778.406 1720.96 L778.687 1720.96 L778.687 1720.96 L778.406 1720.96 L778.406 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="778.406,1720.96 778.406,1720.96 778.687,1720.96 778.406,1720.96 "/>
<path clip-path="url(#clip322)" d="M778.687 1720.96 L778.687 1720.96 L778.969 1720.96 L778.969 1720.96 L778.687 1720.96 L778.687 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="778.687,1720.96 778.687,1720.96 778.969,1720.96 778.687,1720.96 "/>
<path clip-path="url(#clip322)" d="M778.969 1720.96 L778.969 1720.96 L779.251 1720.96 L779.251 1720.96 L778.969 1720.96 L778.969 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="778.969,1720.96 778.969,1720.96 779.251,1720.96 778.969,1720.96 "/>
<path clip-path="url(#clip322)" d="M779.251 1720.96 L779.251 1720.96 L779.533 1720.96 L779.533 1720.96 L779.251 1720.96 L779.251 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="779.251,1720.96 779.251,1720.96 779.533,1720.96 779.251,1720.96 "/>
<path clip-path="url(#clip322)" d="M779.533 1720.96 L779.533 1720.96 L779.814 1720.96 L779.814 1720.96 L779.533 1720.96 L779.533 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="779.533,1720.96 779.533,1720.96 779.814,1720.96 779.533,1720.96 "/>
<path clip-path="url(#clip322)" d="M779.814 1720.96 L779.814 1720.96 L780.096 1720.96 L780.096 1720.96 L779.814 1720.96 L779.814 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="779.814,1720.96 779.814,1720.96 780.096,1720.96 779.814,1720.96 "/>
<path clip-path="url(#clip322)" d="M780.096 1720.96 L780.096 1720.96 L780.378 1720.96 L780.378 1720.96 L780.096 1720.96 L780.096 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="780.096,1720.96 780.096,1720.96 780.378,1720.96 780.096,1720.96 "/>
<path clip-path="url(#clip322)" d="M780.378 1720.96 L780.378 1720.96 L780.659 1720.96 L780.659 1720.96 L780.378 1720.96 L780.378 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="780.378,1720.96 780.378,1720.96 780.659,1720.96 780.378,1720.96 "/>
<path clip-path="url(#clip322)" d="M780.659 1720.96 L780.659 1720.96 L780.941 1720.96 L780.941 1720.96 L780.659 1720.96 L780.659 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="780.659,1720.96 780.659,1720.96 780.941,1720.96 780.659,1720.96 "/>
<path clip-path="url(#clip322)" d="M780.941 1720.96 L780.941 1720.96 L781.223 1720.96 L781.223 1720.96 L780.941 1720.96 L780.941 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="780.941,1720.96 780.941,1720.96 781.223,1720.96 780.941,1720.96 "/>
<path clip-path="url(#clip322)" d="M781.223 1720.96 L781.223 1720.96 L781.505 1720.96 L781.505 1720.96 L781.223 1720.96 L781.223 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="781.223,1720.96 781.223,1720.96 781.505,1720.96 781.223,1720.96 "/>
<path clip-path="url(#clip322)" d="M781.505 1720.96 L781.505 1720.96 L781.786 1720.96 L781.786 1720.96 L781.505 1720.96 L781.505 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="781.505,1720.96 781.505,1720.96 781.786,1720.96 781.505,1720.96 "/>
<path clip-path="url(#clip322)" d="M781.786 1720.96 L781.786 1720.96 L782.068 1720.96 L782.068 1720.96 L781.786 1720.96 L781.786 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="781.786,1720.96 781.786,1720.96 782.068,1720.96 781.786,1720.96 "/>
<path clip-path="url(#clip322)" d="M782.068 1720.96 L782.068 1720.96 L782.35 1720.96 L782.35 1720.96 L782.068 1720.96 L782.068 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="782.068,1720.96 782.068,1720.96 782.35,1720.96 782.068,1720.96 "/>
<path clip-path="url(#clip322)" d="M782.35 1720.96 L782.35 1720.96 L782.632 1720.96 L782.632 1720.96 L782.35 1720.96 L782.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="782.35,1720.96 782.35,1720.96 782.632,1720.96 782.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M782.632 1720.96 L782.632 1720.96 L782.913 1720.96 L782.913 1720.96 L782.632 1720.96 L782.632 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="782.632,1720.96 782.632,1720.96 782.913,1720.96 782.632,1720.96 "/>
<path clip-path="url(#clip322)" d="M782.913 1720.96 L782.913 1720.96 L783.195 1720.96 L783.195 1720.96 L782.913 1720.96 L782.913 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="782.913,1720.96 782.913,1720.96 783.195,1720.96 782.913,1720.96 "/>
<path clip-path="url(#clip322)" d="M783.195 1720.96 L783.195 1720.96 L783.477 1720.96 L783.477 1720.96 L783.195 1720.96 L783.195 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="783.195,1720.96 783.195,1720.96 783.477,1720.96 783.195,1720.96 "/>
<path clip-path="url(#clip322)" d="M783.477 1720.96 L783.477 1720.96 L783.758 1720.96 L783.758 1720.96 L783.477 1720.96 L783.477 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="783.477,1720.96 783.477,1720.96 783.758,1720.96 783.477,1720.96 "/>
<path clip-path="url(#clip322)" d="M783.758 1720.96 L783.758 1720.96 L784.04 1720.96 L784.04 1720.96 L783.758 1720.96 L783.758 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="783.758,1720.96 783.758,1720.96 784.04,1720.96 783.758,1720.96 "/>
<path clip-path="url(#clip322)" d="M784.04 1720.96 L784.04 1720.96 L784.322 1720.96 L784.322 1720.96 L784.04 1720.96 L784.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="784.04,1720.96 784.04,1720.96 784.322,1720.96 784.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M784.322 1720.96 L784.322 1720.96 L784.604 1720.96 L784.604 1720.96 L784.322 1720.96 L784.322 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="784.322,1720.96 784.322,1720.96 784.604,1720.96 784.322,1720.96 "/>
<path clip-path="url(#clip322)" d="M784.604 1720.96 L784.604 1720.96 L784.885 1720.96 L784.885 1720.96 L784.604 1720.96 L784.604 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="784.604,1720.96 784.604,1720.96 784.885,1720.96 784.604,1720.96 "/>
<path clip-path="url(#clip322)" d="M784.885 1720.96 L784.885 1720.96 L785.167 1720.96 L785.167 1720.96 L784.885 1720.96 L784.885 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="784.885,1720.96 784.885,1720.96 785.167,1720.96 784.885,1720.96 "/>
<path clip-path="url(#clip322)" d="M785.167 1720.96 L785.167 1720.96 L785.449 1720.96 L785.449 1720.96 L785.167 1720.96 L785.167 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="785.167,1720.96 785.167,1720.96 785.449,1720.96 785.167,1720.96 "/>
<path clip-path="url(#clip322)" d="M785.449 1720.96 L785.449 1720.96 L785.731 1720.96 L785.731 1720.96 L785.449 1720.96 L785.449 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="785.449,1720.96 785.449,1720.96 785.731,1720.96 785.449,1720.96 "/>
<path clip-path="url(#clip322)" d="M785.731 1720.96 L785.731 1720.96 L786.012 1720.96 L786.012 1720.96 L785.731 1720.96 L785.731 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="785.731,1720.96 785.731,1720.96 786.012,1720.96 785.731,1720.96 "/>
<path clip-path="url(#clip322)" d="M786.012 1720.96 L786.012 1720.96 L786.294 1720.96 L786.294 1720.96 L786.012 1720.96 L786.012 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="786.012,1720.96 786.012,1720.96 786.294,1720.96 786.012,1720.96 "/>
<path clip-path="url(#clip322)" d="M786.294 1720.96 L786.294 1720.96 L786.576 1720.96 L786.576 1720.96 L786.294 1720.96 L786.294 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="786.294,1720.96 786.294,1720.96 786.576,1720.96 786.294,1720.96 "/>
<path clip-path="url(#clip322)" d="M786.576 1720.96 L786.576 1720.96 L786.857 1720.96 L786.857 1720.96 L786.576 1720.96 L786.576 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="786.576,1720.96 786.576,1720.96 786.857,1720.96 786.576,1720.96 "/>
<path clip-path="url(#clip322)" d="M786.857 1720.96 L786.857 1720.96 L787.139 1720.96 L787.139 1720.96 L786.857 1720.96 L786.857 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="786.857,1720.96 786.857,1720.96 787.139,1720.96 786.857,1720.96 "/>
<path clip-path="url(#clip322)" d="M787.139 1720.96 L787.139 1720.96 L787.421 1720.96 L787.421 1720.96 L787.139 1720.96 L787.139 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="787.139,1720.96 787.139,1720.96 787.421,1720.96 787.139,1720.96 "/>
<path clip-path="url(#clip322)" d="M787.421 1720.96 L787.421 1720.96 L787.703 1720.96 L787.703 1720.96 L787.421 1720.96 L787.421 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="787.421,1720.96 787.421,1720.96 787.703,1720.96 787.421,1720.96 "/>
<path clip-path="url(#clip322)" d="M787.703 1720.96 L787.703 1720.96 L787.984 1720.96 L787.984 1720.96 L787.703 1720.96 L787.703 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="787.703,1720.96 787.703,1720.96 787.984,1720.96 787.703,1720.96 "/>
<path clip-path="url(#clip322)" d="M787.984 1720.96 L787.984 1720.96 L788.266 1720.96 L788.266 1720.96 L787.984 1720.96 L787.984 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="787.984,1720.96 787.984,1720.96 788.266,1720.96 787.984,1720.96 "/>
<path clip-path="url(#clip322)" d="M788.266 1720.96 L788.266 1720.96 L788.548 1720.96 L788.548 1720.96 L788.266 1720.96 L788.266 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="788.266,1720.96 788.266,1720.96 788.548,1720.96 788.266,1720.96 "/>
<path clip-path="url(#clip322)" d="M788.548 1720.96 L788.548 1720.96 L788.83 1720.96 L788.83 1720.96 L788.548 1720.96 L788.548 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="788.548,1720.96 788.548,1720.96 788.83,1720.96 788.548,1720.96 "/>
<path clip-path="url(#clip322)" d="M788.83 1720.96 L788.83 1720.96 L789.111 1720.96 L789.111 1720.96 L788.83 1720.96 L788.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="788.83,1720.96 788.83,1720.96 789.111,1720.96 788.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M789.111 1720.96 L789.111 1720.96 L789.393 1720.96 L789.393 1720.96 L789.111 1720.96 L789.111 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="789.111,1720.96 789.111,1720.96 789.393,1720.96 789.111,1720.96 "/>
<path clip-path="url(#clip322)" d="M789.393 1720.96 L789.393 1720.96 L789.675 1720.96 L789.675 1720.96 L789.393 1720.96 L789.393 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="789.393,1720.96 789.393,1720.96 789.675,1720.96 789.393,1720.96 "/>
<path clip-path="url(#clip322)" d="M789.675 1720.96 L789.675 1720.96 L789.956 1720.96 L789.956 1720.96 L789.675 1720.96 L789.675 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="789.675,1720.96 789.675,1720.96 789.956,1720.96 789.675,1720.96 "/>
<path clip-path="url(#clip322)" d="M789.956 1720.96 L789.956 1720.96 L790.238 1720.96 L790.238 1720.96 L789.956 1720.96 L789.956 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="789.956,1720.96 789.956,1720.96 790.238,1720.96 789.956,1720.96 "/>
<path clip-path="url(#clip322)" d="M790.238 1720.96 L790.238 1720.96 L790.52 1720.96 L790.52 1720.96 L790.238 1720.96 L790.238 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="790.238,1720.96 790.238,1720.96 790.52,1720.96 790.238,1720.96 "/>
<path clip-path="url(#clip322)" d="M790.52 1720.96 L790.52 1720.96 L790.802 1720.96 L790.802 1720.96 L790.52 1720.96 L790.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="790.52,1720.96 790.52,1720.96 790.802,1720.96 790.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M790.802 1720.96 L790.802 1720.96 L791.083 1720.96 L791.083 1720.96 L790.802 1720.96 L790.802 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="790.802,1720.96 790.802,1720.96 791.083,1720.96 790.802,1720.96 "/>
<path clip-path="url(#clip322)" d="M791.083 1720.96 L791.083 1720.96 L791.365 1720.96 L791.365 1720.96 L791.083 1720.96 L791.083 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="791.083,1720.96 791.083,1720.96 791.365,1720.96 791.083,1720.96 "/>
<path clip-path="url(#clip322)" d="M791.365 1720.96 L791.365 1720.96 L791.647 1720.96 L791.647 1720.96 L791.365 1720.96 L791.365 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="791.365,1720.96 791.365,1720.96 791.647,1720.96 791.365,1720.96 "/>
<path clip-path="url(#clip322)" d="M791.647 1720.96 L791.647 1720.96 L791.928 1720.96 L791.928 1720.96 L791.647 1720.96 L791.647 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="791.647,1720.96 791.647,1720.96 791.928,1720.96 791.647,1720.96 "/>
<path clip-path="url(#clip322)" d="M791.928 1720.96 L791.928 1720.96 L792.21 1720.96 L792.21 1720.96 L791.928 1720.96 L791.928 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="791.928,1720.96 791.928,1720.96 792.21,1720.96 791.928,1720.96 "/>
<path clip-path="url(#clip322)" d="M792.21 1720.96 L792.21 1720.96 L792.492 1720.96 L792.492 1720.96 L792.21 1720.96 L792.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="792.21,1720.96 792.21,1720.96 792.492,1720.96 792.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M792.492 1720.96 L792.492 1720.96 L792.774 1720.96 L792.774 1720.96 L792.492 1720.96 L792.492 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="792.492,1720.96 792.492,1720.96 792.774,1720.96 792.492,1720.96 "/>
<path clip-path="url(#clip322)" d="M792.774 1720.96 L792.774 1720.96 L793.055 1720.96 L793.055 1720.96 L792.774 1720.96 L792.774 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="792.774,1720.96 792.774,1720.96 793.055,1720.96 792.774,1720.96 "/>
<path clip-path="url(#clip322)" d="M793.055 1720.96 L793.055 1720.96 L793.337 1720.96 L793.337 1720.96 L793.055 1720.96 L793.055 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="793.055,1720.96 793.055,1720.96 793.337,1720.96 793.055,1720.96 "/>
<path clip-path="url(#clip322)" d="M793.337 1720.96 L793.337 1720.96 L793.619 1720.96 L793.619 1720.96 L793.337 1720.96 L793.337 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="793.337,1720.96 793.337,1720.96 793.619,1720.96 793.337,1720.96 "/>
<path clip-path="url(#clip322)" d="M793.619 1720.96 L793.619 1720.96 L793.901 1720.96 L793.901 1720.96 L793.619 1720.96 L793.619 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="793.619,1720.96 793.619,1720.96 793.901,1720.96 793.619,1720.96 "/>
<path clip-path="url(#clip322)" d="M793.901 1720.96 L793.901 1720.96 L794.182 1720.96 L794.182 1720.96 L793.901 1720.96 L793.901 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="793.901,1720.96 793.901,1720.96 794.182,1720.96 793.901,1720.96 "/>
<path clip-path="url(#clip322)" d="M794.182 1720.96 L794.182 1720.96 L794.464 1720.96 L794.464 1720.96 L794.182 1720.96 L794.182 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="794.182,1720.96 794.182,1720.96 794.464,1720.96 794.182,1720.96 "/>
<path clip-path="url(#clip322)" d="M794.464 1720.96 L794.464 1720.96 L794.746 1720.96 L794.746 1720.96 L794.464 1720.96 L794.464 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="794.464,1720.96 794.464,1720.96 794.746,1720.96 794.464,1720.96 "/>
<path clip-path="url(#clip322)" d="M794.746 1720.96 L794.746 1720.96 L795.027 1720.96 L795.027 1720.96 L794.746 1720.96 L794.746 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="794.746,1720.96 794.746,1720.96 795.027,1720.96 794.746,1720.96 "/>
<path clip-path="url(#clip322)" d="M795.027 1720.96 L795.027 1720.96 L795.309 1720.96 L795.309 1720.96 L795.027 1720.96 L795.027 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="795.027,1720.96 795.027,1720.96 795.309,1720.96 795.027,1720.96 "/>
<path clip-path="url(#clip322)" d="M795.309 1720.96 L795.309 1720.96 L795.591 1720.96 L795.591 1720.96 L795.309 1720.96 L795.309 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="795.309,1720.96 795.309,1720.96 795.591,1720.96 795.309,1720.96 "/>
<path clip-path="url(#clip322)" d="M795.591 1720.96 L795.591 1720.96 L795.873 1720.96 L795.873 1720.96 L795.591 1720.96 L795.591 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="795.591,1720.96 795.591,1720.96 795.873,1720.96 795.591,1720.96 "/>
<path clip-path="url(#clip322)" d="M795.873 1720.96 L795.873 1720.96 L796.154 1720.96 L796.154 1720.96 L795.873 1720.96 L795.873 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="795.873,1720.96 795.873,1720.96 796.154,1720.96 795.873,1720.96 "/>
<path clip-path="url(#clip322)" d="M796.154 1720.96 L796.154 1720.96 L796.436 1720.96 L796.436 1720.96 L796.154 1720.96 L796.154 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="796.154,1720.96 796.154,1720.96 796.436,1720.96 796.154,1720.96 "/>
<path clip-path="url(#clip322)" d="M796.436 1720.96 L796.436 1720.96 L796.718 1720.96 L796.718 1720.96 L796.436 1720.96 L796.436 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="796.436,1720.96 796.436,1720.96 796.718,1720.96 796.436,1720.96 "/>
<path clip-path="url(#clip322)" d="M796.718 1720.96 L796.718 1720.96 L797 1720.96 L797 1720.96 L796.718 1720.96 L796.718 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="796.718,1720.96 796.718,1720.96 797,1720.96 796.718,1720.96 "/>
<path clip-path="url(#clip322)" d="M797 1720.96 L797 1720.96 L797.281 1720.96 L797.281 1720.96 L797 1720.96 L797 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="797,1720.96 797,1720.96 797.281,1720.96 797,1720.96 "/>
<path clip-path="url(#clip322)" d="M797.281 1720.96 L797.281 1720.96 L797.563 1720.96 L797.563 1720.96 L797.281 1720.96 L797.281 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="797.281,1720.96 797.281,1720.96 797.563,1720.96 797.281,1720.96 "/>
<path clip-path="url(#clip322)" d="M797.563 1720.96 L797.563 1720.96 L797.845 1720.96 L797.845 1720.96 L797.563 1720.96 L797.563 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="797.563,1720.96 797.563,1720.96 797.845,1720.96 797.563,1720.96 "/>
<path clip-path="url(#clip322)" d="M797.845 1720.96 L797.845 1720.96 L798.126 1720.96 L798.126 1720.96 L797.845 1720.96 L797.845 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="797.845,1720.96 797.845,1720.96 798.126,1720.96 797.845,1720.96 "/>
<path clip-path="url(#clip322)" d="M798.126 1720.96 L798.126 1720.96 L798.408 1720.96 L798.408 1720.96 L798.126 1720.96 L798.126 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="798.126,1720.96 798.126,1720.96 798.408,1720.96 798.126,1720.96 "/>
<path clip-path="url(#clip322)" d="M798.408 1720.96 L798.408 1720.96 L798.69 1720.96 L798.69 1720.96 L798.408 1720.96 L798.408 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="798.408,1720.96 798.408,1720.96 798.69,1720.96 798.408,1720.96 "/>
<path clip-path="url(#clip322)" d="M798.69 1720.96 L798.69 1720.96 L798.972 1720.96 L798.972 1720.96 L798.69 1720.96 L798.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="798.69,1720.96 798.69,1720.96 798.972,1720.96 798.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M798.972 1720.96 L798.972 1720.96 L799.253 1720.96 L799.253 1720.96 L798.972 1720.96 L798.972 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="798.972,1720.96 798.972,1720.96 799.253,1720.96 798.972,1720.96 "/>
<path clip-path="url(#clip322)" d="M799.253 1720.96 L799.253 1720.96 L799.535 1720.96 L799.535 1720.96 L799.253 1720.96 L799.253 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="799.253,1720.96 799.253,1720.96 799.535,1720.96 799.253,1720.96 "/>
<path clip-path="url(#clip322)" d="M799.535 1720.96 L799.535 1720.96 L799.817 1720.96 L799.817 1720.96 L799.535 1720.96 L799.535 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="799.535,1720.96 799.535,1720.96 799.817,1720.96 799.535,1720.96 "/>
<path clip-path="url(#clip322)" d="M799.817 1720.96 L799.817 1720.96 L800.099 1720.96 L800.099 1720.96 L799.817 1720.96 L799.817 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="799.817,1720.96 799.817,1720.96 800.099,1720.96 799.817,1720.96 "/>
<path clip-path="url(#clip322)" d="M800.099 1720.96 L800.099 1720.96 L800.38 1720.96 L800.38 1720.96 L800.099 1720.96 L800.099 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="800.099,1720.96 800.099,1720.96 800.38,1720.96 800.099,1720.96 "/>
<path clip-path="url(#clip322)" d="M800.38 1720.96 L800.38 1720.96 L800.662 1720.96 L800.662 1720.96 L800.38 1720.96 L800.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="800.38,1720.96 800.38,1720.96 800.662,1720.96 800.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M800.662 1720.96 L800.662 1720.96 L800.944 1720.96 L800.944 1720.96 L800.662 1720.96 L800.662 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="800.662,1720.96 800.662,1720.96 800.944,1720.96 800.662,1720.96 "/>
<path clip-path="url(#clip322)" d="M800.944 1720.96 L800.944 1720.96 L801.225 1720.96 L801.225 1720.96 L800.944 1720.96 L800.944 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="800.944,1720.96 800.944,1720.96 801.225,1720.96 800.944,1720.96 "/>
<path clip-path="url(#clip322)" d="M801.225 1720.96 L801.225 1720.96 L801.507 1720.96 L801.507 1720.96 L801.225 1720.96 L801.225 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="801.225,1720.96 801.225,1720.96 801.507,1720.96 801.225,1720.96 "/>
<path clip-path="url(#clip322)" d="M801.507 1720.96 L801.507 1720.96 L801.789 1720.96 L801.789 1720.96 L801.507 1720.96 L801.507 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="801.507,1720.96 801.507,1720.96 801.789,1720.96 801.507,1720.96 "/>
<path clip-path="url(#clip322)" d="M801.789 1720.96 L801.789 1720.96 L802.071 1720.96 L802.071 1720.96 L801.789 1720.96 L801.789 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="801.789,1720.96 801.789,1720.96 802.071,1720.96 801.789,1720.96 "/>
<path clip-path="url(#clip322)" d="M802.071 1720.96 L802.071 1720.96 L802.352 1720.96 L802.352 1720.96 L802.071 1720.96 L802.071 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="802.071,1720.96 802.071,1720.96 802.352,1720.96 802.071,1720.96 "/>
<path clip-path="url(#clip322)" d="M802.352 1720.96 L802.352 1720.96 L802.634 1720.96 L802.634 1720.96 L802.352 1720.96 L802.352 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="802.352,1720.96 802.352,1720.96 802.634,1720.96 802.352,1720.96 "/>
<path clip-path="url(#clip322)" d="M802.634 1720.96 L802.634 1720.96 L802.916 1720.96 L802.916 1720.96 L802.634 1720.96 L802.634 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="802.634,1720.96 802.634,1720.96 802.916,1720.96 802.634,1720.96 "/>
<path clip-path="url(#clip322)" d="M802.916 1720.96 L802.916 1720.96 L803.198 1720.96 L803.198 1720.96 L802.916 1720.96 L802.916 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="802.916,1720.96 802.916,1720.96 803.198,1720.96 802.916,1720.96 "/>
<path clip-path="url(#clip322)" d="M803.198 1720.96 L803.198 1720.96 L803.479 1720.96 L803.479 1720.96 L803.198 1720.96 L803.198 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="803.198,1720.96 803.198,1720.96 803.479,1720.96 803.198,1720.96 "/>
<path clip-path="url(#clip322)" d="M803.479 1720.96 L803.479 1720.96 L803.761 1720.96 L803.761 1720.96 L803.479 1720.96 L803.479 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="803.479,1720.96 803.479,1720.96 803.761,1720.96 803.479,1720.96 "/>
<path clip-path="url(#clip322)" d="M803.761 1720.96 L803.761 1720.96 L804.043 1720.96 L804.043 1720.96 L803.761 1720.96 L803.761 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="803.761,1720.96 803.761,1720.96 804.043,1720.96 803.761,1720.96 "/>
<path clip-path="url(#clip322)" d="M804.043 1720.96 L804.043 1720.96 L804.324 1720.96 L804.324 1720.96 L804.043 1720.96 L804.043 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="804.043,1720.96 804.043,1720.96 804.324,1720.96 804.043,1720.96 "/>
<path clip-path="url(#clip322)" d="M804.324 1720.96 L804.324 1720.96 L804.606 1720.96 L804.606 1720.96 L804.324 1720.96 L804.324 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="804.324,1720.96 804.324,1720.96 804.606,1720.96 804.324,1720.96 "/>
<path clip-path="url(#clip322)" d="M804.606 1720.96 L804.606 1720.96 L804.888 1720.96 L804.888 1720.96 L804.606 1720.96 L804.606 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="804.606,1720.96 804.606,1720.96 804.888,1720.96 804.606,1720.96 "/>
<path clip-path="url(#clip322)" d="M804.888 1720.96 L804.888 1720.96 L805.17 1720.96 L805.17 1720.96 L804.888 1720.96 L804.888 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="804.888,1720.96 804.888,1720.96 805.17,1720.96 804.888,1720.96 "/>
<path clip-path="url(#clip322)" d="M805.17 1720.96 L805.17 1720.96 L805.451 1720.96 L805.451 1720.96 L805.17 1720.96 L805.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="805.17,1720.96 805.17,1720.96 805.451,1720.96 805.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M805.451 1720.96 L805.451 1720.96 L805.733 1720.96 L805.733 1720.96 L805.451 1720.96 L805.451 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="805.451,1720.96 805.451,1720.96 805.733,1720.96 805.451,1720.96 "/>
<path clip-path="url(#clip322)" d="M805.733 1720.96 L805.733 1720.96 L806.015 1720.96 L806.015 1720.96 L805.733 1720.96 L805.733 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="805.733,1720.96 805.733,1720.96 806.015,1720.96 805.733,1720.96 "/>
<path clip-path="url(#clip322)" d="M806.015 1720.96 L806.015 1720.96 L806.296 1720.96 L806.296 1720.96 L806.015 1720.96 L806.015 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="806.015,1720.96 806.015,1720.96 806.296,1720.96 806.015,1720.96 "/>
<path clip-path="url(#clip322)" d="M806.296 1720.96 L806.296 1720.96 L806.578 1720.96 L806.578 1720.96 L806.296 1720.96 L806.296 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="806.296,1720.96 806.296,1720.96 806.578,1720.96 806.296,1720.96 "/>
<path clip-path="url(#clip322)" d="M806.578 1720.96 L806.578 1720.96 L806.86 1720.96 L806.86 1720.96 L806.578 1720.96 L806.578 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="806.578,1720.96 806.578,1720.96 806.86,1720.96 806.578,1720.96 "/>
<path clip-path="url(#clip322)" d="M806.86 1720.96 L806.86 1720.96 L807.142 1720.96 L807.142 1720.96 L806.86 1720.96 L806.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="806.86,1720.96 806.86,1720.96 807.142,1720.96 806.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M807.142 1720.96 L807.142 1720.96 L807.423 1720.96 L807.423 1720.96 L807.142 1720.96 L807.142 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="807.142,1720.96 807.142,1720.96 807.423,1720.96 807.142,1720.96 "/>
<path clip-path="url(#clip322)" d="M807.423 1720.96 L807.423 1720.96 L807.705 1720.96 L807.705 1720.96 L807.423 1720.96 L807.423 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="807.423,1720.96 807.423,1720.96 807.705,1720.96 807.423,1720.96 "/>
<path clip-path="url(#clip322)" d="M807.705 1720.96 L807.705 1720.96 L807.987 1720.96 L807.987 1720.96 L807.705 1720.96 L807.705 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="807.705,1720.96 807.705,1720.96 807.987,1720.96 807.705,1720.96 "/>
<path clip-path="url(#clip322)" d="M807.987 1720.96 L807.987 1720.96 L808.269 1720.96 L808.269 1720.96 L807.987 1720.96 L807.987 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="807.987,1720.96 807.987,1720.96 808.269,1720.96 807.987,1720.96 "/>
<path clip-path="url(#clip322)" d="M808.269 1720.96 L808.269 1720.96 L808.55 1720.96 L808.55 1720.96 L808.269 1720.96 L808.269 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="808.269,1720.96 808.269,1720.96 808.55,1720.96 808.269,1720.96 "/>
<path clip-path="url(#clip322)" d="M808.55 1720.96 L808.55 1720.96 L808.832 1720.96 L808.832 1720.96 L808.55 1720.96 L808.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="808.55,1720.96 808.55,1720.96 808.832,1720.96 808.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M808.832 1720.96 L808.832 1720.96 L809.114 1720.96 L809.114 1720.96 L808.832 1720.96 L808.832 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="808.832,1720.96 808.832,1720.96 809.114,1720.96 808.832,1720.96 "/>
<path clip-path="url(#clip322)" d="M809.114 1720.96 L809.114 1720.96 L809.395 1720.96 L809.395 1720.96 L809.114 1720.96 L809.114 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="809.114,1720.96 809.114,1720.96 809.395,1720.96 809.114,1720.96 "/>
<path clip-path="url(#clip322)" d="M809.395 1720.96 L809.395 1720.96 L809.677 1720.96 L809.677 1720.96 L809.395 1720.96 L809.395 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="809.395,1720.96 809.395,1720.96 809.677,1720.96 809.395,1720.96 "/>
<path clip-path="url(#clip322)" d="M809.677 1720.96 L809.677 1720.96 L809.959 1720.96 L809.959 1720.96 L809.677 1720.96 L809.677 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="809.677,1720.96 809.677,1720.96 809.959,1720.96 809.677,1720.96 "/>
<path clip-path="url(#clip322)" d="M809.959 1720.96 L809.959 1720.96 L810.241 1720.96 L810.241 1720.96 L809.959 1720.96 L809.959 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="809.959,1720.96 809.959,1720.96 810.241,1720.96 809.959,1720.96 "/>
<path clip-path="url(#clip322)" d="M810.241 1720.96 L810.241 1720.96 L810.522 1720.96 L810.522 1720.96 L810.241 1720.96 L810.241 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="810.241,1720.96 810.241,1720.96 810.522,1720.96 810.241,1720.96 "/>
<path clip-path="url(#clip322)" d="M810.522 1720.96 L810.522 1720.96 L810.804 1720.96 L810.804 1720.96 L810.522 1720.96 L810.522 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="810.522,1720.96 810.522,1720.96 810.804,1720.96 810.522,1720.96 "/>
<path clip-path="url(#clip322)" d="M810.804 1720.96 L810.804 1720.96 L811.086 1720.96 L811.086 1720.96 L810.804 1720.96 L810.804 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="810.804,1720.96 810.804,1720.96 811.086,1720.96 810.804,1720.96 "/>
<path clip-path="url(#clip322)" d="M811.086 1720.96 L811.086 1720.96 L811.368 1720.96 L811.368 1720.96 L811.086 1720.96 L811.086 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="811.086,1720.96 811.086,1720.96 811.368,1720.96 811.086,1720.96 "/>
<path clip-path="url(#clip322)" d="M811.368 1720.96 L811.368 1720.96 L811.649 1720.96 L811.649 1720.96 L811.368 1720.96 L811.368 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="811.368,1720.96 811.368,1720.96 811.649,1720.96 811.368,1720.96 "/>
<path clip-path="url(#clip322)" d="M811.649 1720.96 L811.649 1720.96 L811.931 1720.96 L811.931 1720.96 L811.649 1720.96 L811.649 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="811.649,1720.96 811.649,1720.96 811.931,1720.96 811.649,1720.96 "/>
<path clip-path="url(#clip322)" d="M811.931 1720.96 L811.931 1720.96 L812.213 1720.96 L812.213 1720.96 L811.931 1720.96 L811.931 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="811.931,1720.96 811.931,1720.96 812.213,1720.96 811.931,1720.96 "/>
<path clip-path="url(#clip322)" d="M812.213 1720.96 L812.213 1720.96 L812.494 1720.96 L812.494 1720.96 L812.213 1720.96 L812.213 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="812.213,1720.96 812.213,1720.96 812.494,1720.96 812.213,1720.96 "/>
<path clip-path="url(#clip322)" d="M812.494 1720.96 L812.494 1720.96 L812.776 1720.96 L812.776 1720.96 L812.494 1720.96 L812.494 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="812.494,1720.96 812.494,1720.96 812.776,1720.96 812.494,1720.96 "/>
<path clip-path="url(#clip322)" d="M812.776 1720.96 L812.776 1720.96 L813.058 1720.96 L813.058 1720.96 L812.776 1720.96 L812.776 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="812.776,1720.96 812.776,1720.96 813.058,1720.96 812.776,1720.96 "/>
<path clip-path="url(#clip322)" d="M813.058 1720.96 L813.058 1720.96 L813.34 1720.96 L813.34 1720.96 L813.058 1720.96 L813.058 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="813.058,1720.96 813.058,1720.96 813.34,1720.96 813.058,1720.96 "/>
<path clip-path="url(#clip322)" d="M813.34 1720.96 L813.34 1720.96 L813.621 1720.96 L813.621 1720.96 L813.34 1720.96 L813.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="813.34,1720.96 813.34,1720.96 813.621,1720.96 813.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M813.621 1720.96 L813.621 1720.96 L813.903 1720.96 L813.903 1720.96 L813.621 1720.96 L813.621 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="813.621,1720.96 813.621,1720.96 813.903,1720.96 813.621,1720.96 "/>
<path clip-path="url(#clip322)" d="M813.903 1720.96 L813.903 1720.96 L814.185 1720.96 L814.185 1720.96 L813.903 1720.96 L813.903 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="813.903,1720.96 813.903,1720.96 814.185,1720.96 813.903,1720.96 "/>
<path clip-path="url(#clip322)" d="M814.185 1720.96 L814.185 1720.96 L814.467 1720.96 L814.467 1720.96 L814.185 1720.96 L814.185 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="814.185,1720.96 814.185,1720.96 814.467,1720.96 814.185,1720.96 "/>
<path clip-path="url(#clip322)" d="M814.467 1720.96 L814.467 1720.96 L814.748 1720.96 L814.748 1720.96 L814.467 1720.96 L814.467 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="814.467,1720.96 814.467,1720.96 814.748,1720.96 814.467,1720.96 "/>
<path clip-path="url(#clip322)" d="M814.748 1720.96 L814.748 1720.96 L815.03 1720.96 L815.03 1720.96 L814.748 1720.96 L814.748 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="814.748,1720.96 814.748,1720.96 815.03,1720.96 814.748,1720.96 "/>
<path clip-path="url(#clip322)" d="M815.03 1720.96 L815.03 1720.96 L815.312 1720.96 L815.312 1720.96 L815.03 1720.96 L815.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="815.03,1720.96 815.03,1720.96 815.312,1720.96 815.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M815.312 1720.96 L815.312 1720.96 L815.593 1720.96 L815.593 1720.96 L815.312 1720.96 L815.312 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="815.312,1720.96 815.312,1720.96 815.593,1720.96 815.312,1720.96 "/>
<path clip-path="url(#clip322)" d="M815.593 1720.96 L815.593 1720.96 L815.875 1720.96 L815.875 1720.96 L815.593 1720.96 L815.593 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="815.593,1720.96 815.593,1720.96 815.875,1720.96 815.593,1720.96 "/>
<path clip-path="url(#clip322)" d="M815.875 1720.96 L815.875 1720.96 L816.157 1720.96 L816.157 1720.96 L815.875 1720.96 L815.875 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="815.875,1720.96 815.875,1720.96 816.157,1720.96 815.875,1720.96 "/>
<path clip-path="url(#clip322)" d="M816.157 1720.96 L816.157 1720.96 L816.439 1720.96 L816.439 1720.96 L816.157 1720.96 L816.157 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="816.157,1720.96 816.157,1720.96 816.439,1720.96 816.157,1720.96 "/>
<path clip-path="url(#clip322)" d="M816.439 1720.96 L816.439 1720.96 L816.72 1720.96 L816.72 1720.96 L816.439 1720.96 L816.439 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="816.439,1720.96 816.439,1720.96 816.72,1720.96 816.439,1720.96 "/>
<path clip-path="url(#clip322)" d="M816.72 1720.96 L816.72 1720.96 L817.002 1720.96 L817.002 1720.96 L816.72 1720.96 L816.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="816.72,1720.96 816.72,1720.96 817.002,1720.96 816.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M817.002 1720.96 L817.002 1720.96 L817.284 1720.96 L817.284 1720.96 L817.002 1720.96 L817.002 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="817.002,1720.96 817.002,1720.96 817.284,1720.96 817.002,1720.96 "/>
<path clip-path="url(#clip322)" d="M817.284 1720.96 L817.284 1720.96 L817.566 1720.96 L817.566 1720.96 L817.284 1720.96 L817.284 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="817.284,1720.96 817.284,1720.96 817.566,1720.96 817.284,1720.96 "/>
<path clip-path="url(#clip322)" d="M817.566 1720.96 L817.566 1720.96 L817.847 1720.96 L817.847 1720.96 L817.566 1720.96 L817.566 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="817.566,1720.96 817.566,1720.96 817.847,1720.96 817.566,1720.96 "/>
<path clip-path="url(#clip322)" d="M817.847 1720.96 L817.847 1720.96 L818.129 1720.96 L818.129 1720.96 L817.847 1720.96 L817.847 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="817.847,1720.96 817.847,1720.96 818.129,1720.96 817.847,1720.96 "/>
<path clip-path="url(#clip322)" d="M818.129 1720.96 L818.129 1720.96 L818.411 1720.96 L818.411 1720.96 L818.129 1720.96 L818.129 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="818.129,1720.96 818.129,1720.96 818.411,1720.96 818.129,1720.96 "/>
<path clip-path="url(#clip322)" d="M818.411 1720.96 L818.411 1720.96 L818.692 1720.96 L818.692 1720.96 L818.411 1720.96 L818.411 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="818.411,1720.96 818.411,1720.96 818.692,1720.96 818.411,1720.96 "/>
<path clip-path="url(#clip322)" d="M818.692 1720.96 L818.692 1720.96 L818.974 1720.96 L818.974 1720.96 L818.692 1720.96 L818.692 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="818.692,1720.96 818.692,1720.96 818.974,1720.96 818.692,1720.96 "/>
<path clip-path="url(#clip322)" d="M818.974 1720.96 L818.974 1720.96 L819.256 1720.96 L819.256 1720.96 L818.974 1720.96 L818.974 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="818.974,1720.96 818.974,1720.96 819.256,1720.96 818.974,1720.96 "/>
<path clip-path="url(#clip322)" d="M819.256 1720.96 L819.256 1720.96 L819.538 1720.96 L819.538 1720.96 L819.256 1720.96 L819.256 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="819.256,1720.96 819.256,1720.96 819.538,1720.96 819.256,1720.96 "/>
<path clip-path="url(#clip322)" d="M819.538 1720.96 L819.538 1720.96 L819.819 1720.96 L819.819 1720.96 L819.538 1720.96 L819.538 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="819.538,1720.96 819.538,1720.96 819.819,1720.96 819.538,1720.96 "/>
<path clip-path="url(#clip322)" d="M819.819 1720.96 L819.819 1720.96 L820.101 1720.96 L820.101 1720.96 L819.819 1720.96 L819.819 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="819.819,1720.96 819.819,1720.96 820.101,1720.96 819.819,1720.96 "/>
<path clip-path="url(#clip322)" d="M820.101 1720.96 L820.101 1720.96 L820.383 1720.96 L820.383 1720.96 L820.101 1720.96 L820.101 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="820.101,1720.96 820.101,1720.96 820.383,1720.96 820.101,1720.96 "/>
<path clip-path="url(#clip322)" d="M820.383 1720.96 L820.383 1720.96 L820.665 1720.96 L820.665 1720.96 L820.383 1720.96 L820.383 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="820.383,1720.96 820.383,1720.96 820.665,1720.96 820.383,1720.96 "/>
<path clip-path="url(#clip322)" d="M820.665 1720.96 L820.665 1720.96 L820.946 1720.96 L820.946 1720.96 L820.665 1720.96 L820.665 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="820.665,1720.96 820.665,1720.96 820.946,1720.96 820.665,1720.96 "/>
<path clip-path="url(#clip322)" d="M820.946 1720.96 L820.946 1720.96 L821.228 1720.96 L821.228 1720.96 L820.946 1720.96 L820.946 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="820.946,1720.96 820.946,1720.96 821.228,1720.96 820.946,1720.96 "/>
<path clip-path="url(#clip322)" d="M821.228 1720.96 L821.228 1720.96 L821.51 1720.96 L821.51 1720.96 L821.228 1720.96 L821.228 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="821.228,1720.96 821.228,1720.96 821.51,1720.96 821.228,1720.96 "/>
<path clip-path="url(#clip322)" d="M821.51 1720.96 L821.51 1720.96 L821.791 1720.96 L821.791 1720.96 L821.51 1720.96 L821.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="821.51,1720.96 821.51,1720.96 821.791,1720.96 821.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M821.791 1720.96 L821.791 1720.96 L822.073 1720.96 L822.073 1720.96 L821.791 1720.96 L821.791 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="821.791,1720.96 821.791,1720.96 822.073,1720.96 821.791,1720.96 "/>
<path clip-path="url(#clip322)" d="M822.073 1720.96 L822.073 1720.96 L822.355 1720.96 L822.355 1720.96 L822.073 1720.96 L822.073 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="822.073,1720.96 822.073,1720.96 822.355,1720.96 822.073,1720.96 "/>
<path clip-path="url(#clip322)" d="M822.355 1720.96 L822.355 1720.96 L822.637 1720.96 L822.637 1720.96 L822.355 1720.96 L822.355 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="822.355,1720.96 822.355,1720.96 822.637,1720.96 822.355,1720.96 "/>
<path clip-path="url(#clip322)" d="M822.637 1720.96 L822.637 1720.96 L822.918 1720.96 L822.918 1720.96 L822.637 1720.96 L822.637 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="822.637,1720.96 822.637,1720.96 822.918,1720.96 822.637,1720.96 "/>
<path clip-path="url(#clip322)" d="M822.918 1720.96 L822.918 1720.96 L823.2 1720.96 L823.2 1720.96 L822.918 1720.96 L822.918 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="822.918,1720.96 822.918,1720.96 823.2,1720.96 822.918,1720.96 "/>
<path clip-path="url(#clip322)" d="M823.2 1720.96 L823.2 1720.96 L823.482 1720.96 L823.482 1720.96 L823.2 1720.96 L823.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="823.2,1720.96 823.2,1720.96 823.482,1720.96 823.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M823.482 1720.96 L823.482 1720.96 L823.763 1720.96 L823.763 1720.96 L823.482 1720.96 L823.482 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="823.482,1720.96 823.482,1720.96 823.763,1720.96 823.482,1720.96 "/>
<path clip-path="url(#clip322)" d="M823.763 1720.96 L823.763 1720.96 L824.045 1720.96 L824.045 1720.96 L823.763 1720.96 L823.763 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="823.763,1720.96 823.763,1720.96 824.045,1720.96 823.763,1720.96 "/>
<path clip-path="url(#clip322)" d="M824.045 1720.96 L824.045 1720.96 L824.327 1720.96 L824.327 1720.96 L824.045 1720.96 L824.045 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="824.045,1720.96 824.045,1720.96 824.327,1720.96 824.045,1720.96 "/>
<path clip-path="url(#clip322)" d="M824.327 1720.96 L824.327 1720.96 L824.609 1720.96 L824.609 1720.96 L824.327 1720.96 L824.327 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="824.327,1720.96 824.327,1720.96 824.609,1720.96 824.327,1720.96 "/>
<path clip-path="url(#clip322)" d="M824.609 1720.96 L824.609 1720.96 L824.89 1720.96 L824.89 1720.96 L824.609 1720.96 L824.609 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="824.609,1720.96 824.609,1720.96 824.89,1720.96 824.609,1720.96 "/>
<path clip-path="url(#clip322)" d="M824.89 1720.96 L824.89 1720.96 L825.172 1720.96 L825.172 1720.96 L824.89 1720.96 L824.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="824.89,1720.96 824.89,1720.96 825.172,1720.96 824.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M825.172 1720.96 L825.172 1720.96 L825.454 1720.96 L825.454 1720.96 L825.172 1720.96 L825.172 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="825.172,1720.96 825.172,1720.96 825.454,1720.96 825.172,1720.96 "/>
<path clip-path="url(#clip322)" d="M825.454 1720.96 L825.454 1720.96 L825.736 1720.96 L825.736 1720.96 L825.454 1720.96 L825.454 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="825.454,1720.96 825.454,1720.96 825.736,1720.96 825.454,1720.96 "/>
<path clip-path="url(#clip322)" d="M825.736 1720.96 L825.736 1720.96 L826.017 1720.96 L826.017 1720.96 L825.736 1720.96 L825.736 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="825.736,1720.96 825.736,1720.96 826.017,1720.96 825.736,1720.96 "/>
<path clip-path="url(#clip322)" d="M826.017 1720.96 L826.017 1720.96 L826.299 1720.96 L826.299 1720.96 L826.017 1720.96 L826.017 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="826.017,1720.96 826.017,1720.96 826.299,1720.96 826.017,1720.96 "/>
<path clip-path="url(#clip322)" d="M826.299 1720.96 L826.299 1720.96 L826.581 1720.96 L826.581 1720.96 L826.299 1720.96 L826.299 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="826.299,1720.96 826.299,1720.96 826.581,1720.96 826.299,1720.96 "/>
<path clip-path="url(#clip322)" d="M826.581 1720.96 L826.581 1720.96 L826.862 1720.96 L826.862 1720.96 L826.581 1720.96 L826.581 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="826.581,1720.96 826.581,1720.96 826.862,1720.96 826.581,1720.96 "/>
<path clip-path="url(#clip322)" d="M826.862 1720.96 L826.862 1720.96 L827.144 1720.96 L827.144 1720.96 L826.862 1720.96 L826.862 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="826.862,1720.96 826.862,1720.96 827.144,1720.96 826.862,1720.96 "/>
<path clip-path="url(#clip322)" d="M827.144 1720.96 L827.144 1720.96 L827.426 1720.96 L827.426 1720.96 L827.144 1720.96 L827.144 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="827.144,1720.96 827.144,1720.96 827.426,1720.96 827.144,1720.96 "/>
<path clip-path="url(#clip322)" d="M827.426 1720.96 L827.426 1720.96 L827.708 1720.96 L827.708 1720.96 L827.426 1720.96 L827.426 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="827.426,1720.96 827.426,1720.96 827.708,1720.96 827.426,1720.96 "/>
<path clip-path="url(#clip322)" d="M827.708 1720.96 L827.708 1720.96 L827.989 1720.96 L827.989 1720.96 L827.708 1720.96 L827.708 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="827.708,1720.96 827.708,1720.96 827.989,1720.96 827.708,1720.96 "/>
<path clip-path="url(#clip322)" d="M827.989 1720.96 L827.989 1720.96 L828.271 1720.96 L828.271 1720.96 L827.989 1720.96 L827.989 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="827.989,1720.96 827.989,1720.96 828.271,1720.96 827.989,1720.96 "/>
<path clip-path="url(#clip322)" d="M828.271 1720.96 L828.271 1720.96 L828.553 1720.96 L828.553 1720.96 L828.271 1720.96 L828.271 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="828.271,1720.96 828.271,1720.96 828.553,1720.96 828.271,1720.96 "/>
<path clip-path="url(#clip322)" d="M828.553 1720.96 L828.553 1720.96 L828.835 1720.96 L828.835 1720.96 L828.553 1720.96 L828.553 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="828.553,1720.96 828.553,1720.96 828.835,1720.96 828.553,1720.96 "/>
<path clip-path="url(#clip322)" d="M828.835 1720.96 L828.835 1720.96 L829.116 1720.96 L829.116 1720.96 L828.835 1720.96 L828.835 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="828.835,1720.96 828.835,1720.96 829.116,1720.96 828.835,1720.96 "/>
<path clip-path="url(#clip322)" d="M829.116 1720.96 L829.116 1720.96 L829.398 1720.96 L829.398 1720.96 L829.116 1720.96 L829.116 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="829.116,1720.96 829.116,1720.96 829.398,1720.96 829.116,1720.96 "/>
<path clip-path="url(#clip322)" d="M829.398 1720.76 L829.398 1720.96 L829.68 1720.96 L829.68 1720.76 L829.398 1720.76 L829.398 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="829.398,1720.76 829.398,1720.96 829.68,1720.96 829.68,1720.76 829.398,1720.76 "/>
<path clip-path="url(#clip322)" d="M829.68 1720.37 L829.68 1720.96 L829.961 1720.96 L829.961 1720.37 L829.68 1720.37 L829.68 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="829.68,1720.37 829.68,1720.96 829.961,1720.96 829.961,1720.37 829.68,1720.37 "/>
<path clip-path="url(#clip322)" d="M829.961 1720.56 L829.961 1720.96 L830.243 1720.96 L830.243 1720.56 L829.961 1720.56 L829.961 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="829.961,1720.56 829.961,1720.96 830.243,1720.96 830.243,1720.56 829.961,1720.56 "/>
<path clip-path="url(#clip322)" d="M830.243 1719.58 L830.243 1720.96 L830.525 1720.96 L830.525 1719.58 L830.243 1719.58 L830.243 1719.58  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="830.243,1719.58 830.243,1720.96 830.525,1720.96 830.525,1719.58 830.243,1719.58 "/>
<path clip-path="url(#clip322)" d="M830.525 1720.56 L830.525 1720.96 L830.807 1720.96 L830.807 1720.56 L830.525 1720.56 L830.525 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="830.525,1720.56 830.525,1720.96 830.807,1720.96 830.807,1720.56 830.525,1720.56 "/>
<path clip-path="url(#clip322)" d="M830.807 1720.37 L830.807 1720.96 L831.088 1720.96 L831.088 1720.37 L830.807 1720.37 L830.807 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="830.807,1720.37 830.807,1720.96 831.088,1720.96 831.088,1720.37 830.807,1720.37 "/>
<path clip-path="url(#clip322)" d="M831.088 1719.97 L831.088 1720.96 L831.37 1720.96 L831.37 1719.97 L831.088 1719.97 L831.088 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="831.088,1719.97 831.088,1720.96 831.37,1720.96 831.37,1719.97 831.088,1719.97 "/>
<path clip-path="url(#clip322)" d="M831.37 1720.17 L831.37 1720.96 L831.652 1720.96 L831.652 1720.17 L831.37 1720.17 L831.37 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="831.37,1720.17 831.37,1720.96 831.652,1720.96 831.652,1720.17 831.37,1720.17 "/>
<path clip-path="url(#clip322)" d="M831.652 1719.97 L831.652 1720.96 L831.934 1720.96 L831.934 1719.97 L831.652 1719.97 L831.652 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="831.652,1719.97 831.652,1720.96 831.934,1720.96 831.934,1719.97 831.652,1719.97 "/>
<path clip-path="url(#clip322)" d="M831.934 1720.76 L831.934 1720.96 L832.215 1720.96 L832.215 1720.76 L831.934 1720.76 L831.934 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="831.934,1720.76 831.934,1720.96 832.215,1720.96 832.215,1720.76 831.934,1720.76 "/>
<path clip-path="url(#clip322)" d="M832.215 1720.96 L832.215 1720.96 L832.497 1720.96 L832.497 1720.96 L832.215 1720.96 L832.215 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="832.215,1720.96 832.215,1720.96 832.497,1720.96 832.215,1720.96 "/>
<path clip-path="url(#clip322)" d="M832.497 1720.17 L832.497 1720.96 L832.779 1720.96 L832.779 1720.17 L832.497 1720.17 L832.497 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="832.497,1720.17 832.497,1720.96 832.779,1720.96 832.779,1720.17 832.497,1720.17 "/>
<path clip-path="url(#clip322)" d="M832.779 1719.58 L832.779 1720.96 L833.06 1720.96 L833.06 1719.58 L832.779 1719.58 L832.779 1719.58  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="832.779,1719.58 832.779,1720.96 833.06,1720.96 833.06,1719.58 832.779,1719.58 "/>
<path clip-path="url(#clip322)" d="M833.06 1720.56 L833.06 1720.96 L833.342 1720.96 L833.342 1720.56 L833.06 1720.56 L833.06 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="833.06,1720.56 833.06,1720.96 833.342,1720.96 833.342,1720.56 833.06,1720.56 "/>
<path clip-path="url(#clip322)" d="M833.342 1720.17 L833.342 1720.96 L833.624 1720.96 L833.624 1720.17 L833.342 1720.17 L833.342 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="833.342,1720.17 833.342,1720.96 833.624,1720.96 833.624,1720.17 833.342,1720.17 "/>
<path clip-path="url(#clip322)" d="M833.624 1720.17 L833.624 1720.96 L833.906 1720.96 L833.906 1720.17 L833.624 1720.17 L833.624 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="833.624,1720.17 833.624,1720.96 833.906,1720.96 833.906,1720.17 833.624,1720.17 "/>
<path clip-path="url(#clip322)" d="M833.906 1719.78 L833.906 1720.96 L834.187 1720.96 L834.187 1719.78 L833.906 1719.78 L833.906 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="833.906,1719.78 833.906,1720.96 834.187,1720.96 834.187,1719.78 833.906,1719.78 "/>
<path clip-path="url(#clip322)" d="M834.187 1720.17 L834.187 1720.96 L834.469 1720.96 L834.469 1720.17 L834.187 1720.17 L834.187 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="834.187,1720.17 834.187,1720.96 834.469,1720.96 834.469,1720.17 834.187,1720.17 "/>
<path clip-path="url(#clip322)" d="M834.469 1719.78 L834.469 1720.96 L834.751 1720.96 L834.751 1719.78 L834.469 1719.78 L834.469 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="834.469,1719.78 834.469,1720.96 834.751,1720.96 834.751,1719.78 834.469,1719.78 "/>
<path clip-path="url(#clip322)" d="M834.751 1720.37 L834.751 1720.96 L835.033 1720.96 L835.033 1720.37 L834.751 1720.37 L834.751 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="834.751,1720.37 834.751,1720.96 835.033,1720.96 835.033,1720.37 834.751,1720.37 "/>
<path clip-path="url(#clip322)" d="M835.033 1720.37 L835.033 1720.96 L835.314 1720.96 L835.314 1720.37 L835.033 1720.37 L835.033 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="835.033,1720.37 835.033,1720.96 835.314,1720.96 835.314,1720.37 835.033,1720.37 "/>
<path clip-path="url(#clip322)" d="M835.314 1719.78 L835.314 1720.96 L835.596 1720.96 L835.596 1719.78 L835.314 1719.78 L835.314 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="835.314,1719.78 835.314,1720.96 835.596,1720.96 835.596,1719.78 835.314,1719.78 "/>
<path clip-path="url(#clip322)" d="M835.596 1720.17 L835.596 1720.96 L835.878 1720.96 L835.878 1720.17 L835.596 1720.17 L835.596 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="835.596,1720.17 835.596,1720.96 835.878,1720.96 835.878,1720.17 835.596,1720.17 "/>
<path clip-path="url(#clip322)" d="M835.878 1720.56 L835.878 1720.96 L836.159 1720.96 L836.159 1720.56 L835.878 1720.56 L835.878 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="835.878,1720.56 835.878,1720.96 836.159,1720.96 836.159,1720.56 835.878,1720.56 "/>
<path clip-path="url(#clip322)" d="M836.159 1719.19 L836.159 1720.96 L836.441 1720.96 L836.441 1719.19 L836.159 1719.19 L836.159 1719.19  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="836.159,1719.19 836.159,1720.96 836.441,1720.96 836.441,1719.19 836.159,1719.19 "/>
<path clip-path="url(#clip322)" d="M836.441 1719.78 L836.441 1720.96 L836.723 1720.96 L836.723 1719.78 L836.441 1719.78 L836.441 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="836.441,1719.78 836.441,1720.96 836.723,1720.96 836.723,1719.78 836.441,1719.78 "/>
<path clip-path="url(#clip322)" d="M836.723 1720.76 L836.723 1720.96 L837.005 1720.96 L837.005 1720.76 L836.723 1720.76 L836.723 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="836.723,1720.76 836.723,1720.96 837.005,1720.96 837.005,1720.76 836.723,1720.76 "/>
<path clip-path="url(#clip322)" d="M837.005 1720.37 L837.005 1720.96 L837.286 1720.96 L837.286 1720.37 L837.005 1720.37 L837.005 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="837.005,1720.37 837.005,1720.96 837.286,1720.96 837.286,1720.37 837.005,1720.37 "/>
<path clip-path="url(#clip322)" d="M837.286 1719.97 L837.286 1720.96 L837.568 1720.96 L837.568 1719.97 L837.286 1719.97 L837.286 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="837.286,1719.97 837.286,1720.96 837.568,1720.96 837.568,1719.97 837.286,1719.97 "/>
<path clip-path="url(#clip322)" d="M837.568 1720.37 L837.568 1720.96 L837.85 1720.96 L837.85 1720.37 L837.568 1720.37 L837.568 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="837.568,1720.37 837.568,1720.96 837.85,1720.96 837.85,1720.37 837.568,1720.37 "/>
<path clip-path="url(#clip322)" d="M837.85 1720.17 L837.85 1720.96 L838.131 1720.96 L838.131 1720.17 L837.85 1720.17 L837.85 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="837.85,1720.17 837.85,1720.96 838.131,1720.96 838.131,1720.17 837.85,1720.17 "/>
<path clip-path="url(#clip322)" d="M838.131 1720.96 L838.131 1720.96 L838.413 1720.96 L838.413 1720.96 L838.131 1720.96 L838.131 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="838.131,1720.96 838.131,1720.96 838.413,1720.96 838.131,1720.96 "/>
<path clip-path="url(#clip322)" d="M838.413 1720.56 L838.413 1720.96 L838.695 1720.96 L838.695 1720.56 L838.413 1720.56 L838.413 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="838.413,1720.56 838.413,1720.96 838.695,1720.96 838.695,1720.56 838.413,1720.56 "/>
<path clip-path="url(#clip322)" d="M838.695 1719.19 L838.695 1720.96 L838.977 1720.96 L838.977 1719.19 L838.695 1719.19 L838.695 1719.19  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="838.695,1719.19 838.695,1720.96 838.977,1720.96 838.977,1719.19 838.695,1719.19 "/>
<path clip-path="url(#clip322)" d="M838.977 1720.76 L838.977 1720.96 L839.258 1720.96 L839.258 1720.76 L838.977 1720.76 L838.977 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="838.977,1720.76 838.977,1720.96 839.258,1720.96 839.258,1720.76 838.977,1720.76 "/>
<path clip-path="url(#clip322)" d="M839.258 1720.76 L839.258 1720.96 L839.54 1720.96 L839.54 1720.76 L839.258 1720.76 L839.258 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="839.258,1720.76 839.258,1720.96 839.54,1720.96 839.54,1720.76 839.258,1720.76 "/>
<path clip-path="url(#clip322)" d="M839.54 1720.56 L839.54 1720.96 L839.822 1720.96 L839.822 1720.56 L839.54 1720.56 L839.54 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="839.54,1720.56 839.54,1720.96 839.822,1720.96 839.822,1720.56 839.54,1720.56 "/>
<path clip-path="url(#clip322)" d="M839.822 1720.37 L839.822 1720.96 L840.104 1720.96 L840.104 1720.37 L839.822 1720.37 L839.822 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="839.822,1720.37 839.822,1720.96 840.104,1720.96 840.104,1720.37 839.822,1720.37 "/>
<path clip-path="url(#clip322)" d="M840.104 1720.37 L840.104 1720.96 L840.385 1720.96 L840.385 1720.37 L840.104 1720.37 L840.104 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="840.104,1720.37 840.104,1720.96 840.385,1720.96 840.385,1720.37 840.104,1720.37 "/>
<path clip-path="url(#clip322)" d="M840.385 1720.37 L840.385 1720.96 L840.667 1720.96 L840.667 1720.37 L840.385 1720.37 L840.385 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="840.385,1720.37 840.385,1720.96 840.667,1720.96 840.667,1720.37 840.385,1720.37 "/>
<path clip-path="url(#clip322)" d="M840.667 1719.97 L840.667 1720.96 L840.949 1720.96 L840.949 1719.97 L840.667 1719.97 L840.667 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="840.667,1719.97 840.667,1720.96 840.949,1720.96 840.949,1719.97 840.667,1719.97 "/>
<path clip-path="url(#clip322)" d="M840.949 1720.17 L840.949 1720.96 L841.23 1720.96 L841.23 1720.17 L840.949 1720.17 L840.949 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="840.949,1720.17 840.949,1720.96 841.23,1720.96 841.23,1720.17 840.949,1720.17 "/>
<path clip-path="url(#clip322)" d="M841.23 1720.17 L841.23 1720.96 L841.512 1720.96 L841.512 1720.17 L841.23 1720.17 L841.23 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="841.23,1720.17 841.23,1720.96 841.512,1720.96 841.512,1720.17 841.23,1720.17 "/>
<path clip-path="url(#clip322)" d="M841.512 1720.56 L841.512 1720.96 L841.794 1720.96 L841.794 1720.56 L841.512 1720.56 L841.512 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="841.512,1720.56 841.512,1720.96 841.794,1720.96 841.794,1720.56 841.512,1720.56 "/>
<path clip-path="url(#clip322)" d="M841.794 1719.78 L841.794 1720.96 L842.076 1720.96 L842.076 1719.78 L841.794 1719.78 L841.794 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="841.794,1719.78 841.794,1720.96 842.076,1720.96 842.076,1719.78 841.794,1719.78 "/>
<path clip-path="url(#clip322)" d="M842.076 1720.56 L842.076 1720.96 L842.357 1720.96 L842.357 1720.56 L842.076 1720.56 L842.076 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="842.076,1720.56 842.076,1720.96 842.357,1720.96 842.357,1720.56 842.076,1720.56 "/>
<path clip-path="url(#clip322)" d="M842.357 1719.97 L842.357 1720.96 L842.639 1720.96 L842.639 1719.97 L842.357 1719.97 L842.357 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="842.357,1719.97 842.357,1720.96 842.639,1720.96 842.639,1719.97 842.357,1719.97 "/>
<path clip-path="url(#clip322)" d="M842.639 1720.37 L842.639 1720.96 L842.921 1720.96 L842.921 1720.37 L842.639 1720.37 L842.639 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="842.639,1720.37 842.639,1720.96 842.921,1720.96 842.921,1720.37 842.639,1720.37 "/>
<path clip-path="url(#clip322)" d="M842.921 1720.37 L842.921 1720.96 L843.203 1720.96 L843.203 1720.37 L842.921 1720.37 L842.921 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="842.921,1720.37 842.921,1720.96 843.203,1720.96 843.203,1720.37 842.921,1720.37 "/>
<path clip-path="url(#clip322)" d="M843.203 1720.56 L843.203 1720.96 L843.484 1720.96 L843.484 1720.56 L843.203 1720.56 L843.203 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="843.203,1720.56 843.203,1720.96 843.484,1720.96 843.484,1720.56 843.203,1720.56 "/>
<path clip-path="url(#clip322)" d="M843.484 1720.17 L843.484 1720.96 L843.766 1720.96 L843.766 1720.17 L843.484 1720.17 L843.484 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="843.484,1720.17 843.484,1720.96 843.766,1720.96 843.766,1720.17 843.484,1720.17 "/>
<path clip-path="url(#clip322)" d="M843.766 1720.37 L843.766 1720.96 L844.048 1720.96 L844.048 1720.37 L843.766 1720.37 L843.766 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="843.766,1720.37 843.766,1720.96 844.048,1720.96 844.048,1720.37 843.766,1720.37 "/>
<path clip-path="url(#clip322)" d="M844.048 1720.56 L844.048 1720.96 L844.329 1720.96 L844.329 1720.56 L844.048 1720.56 L844.048 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="844.048,1720.56 844.048,1720.96 844.329,1720.96 844.329,1720.56 844.048,1720.56 "/>
<path clip-path="url(#clip322)" d="M844.329 1720.56 L844.329 1720.96 L844.611 1720.96 L844.611 1720.56 L844.329 1720.56 L844.329 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="844.329,1720.56 844.329,1720.96 844.611,1720.96 844.611,1720.56 844.329,1720.56 "/>
<path clip-path="url(#clip322)" d="M844.611 1720.76 L844.611 1720.96 L844.893 1720.96 L844.893 1720.76 L844.611 1720.76 L844.611 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="844.611,1720.76 844.611,1720.96 844.893,1720.96 844.893,1720.76 844.611,1720.76 "/>
<path clip-path="url(#clip322)" d="M844.893 1720.17 L844.893 1720.96 L845.175 1720.96 L845.175 1720.17 L844.893 1720.17 L844.893 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="844.893,1720.17 844.893,1720.96 845.175,1720.96 845.175,1720.17 844.893,1720.17 "/>
<path clip-path="url(#clip322)" d="M845.175 1719.97 L845.175 1720.96 L845.456 1720.96 L845.456 1719.97 L845.175 1719.97 L845.175 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="845.175,1719.97 845.175,1720.96 845.456,1720.96 845.456,1719.97 845.175,1719.97 "/>
<path clip-path="url(#clip322)" d="M845.456 1719.97 L845.456 1720.96 L845.738 1720.96 L845.738 1719.97 L845.456 1719.97 L845.456 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="845.456,1719.97 845.456,1720.96 845.738,1720.96 845.738,1719.97 845.456,1719.97 "/>
<path clip-path="url(#clip322)" d="M845.738 1720.56 L845.738 1720.96 L846.02 1720.96 L846.02 1720.56 L845.738 1720.56 L845.738 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="845.738,1720.56 845.738,1720.96 846.02,1720.96 846.02,1720.56 845.738,1720.56 "/>
<path clip-path="url(#clip322)" d="M846.02 1720.37 L846.02 1720.96 L846.302 1720.96 L846.302 1720.37 L846.02 1720.37 L846.02 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="846.02,1720.37 846.02,1720.96 846.302,1720.96 846.302,1720.37 846.02,1720.37 "/>
<path clip-path="url(#clip322)" d="M846.302 1720.37 L846.302 1720.96 L846.583 1720.96 L846.583 1720.37 L846.302 1720.37 L846.302 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="846.302,1720.37 846.302,1720.96 846.583,1720.96 846.583,1720.37 846.302,1720.37 "/>
<path clip-path="url(#clip322)" d="M846.583 1720.76 L846.583 1720.96 L846.865 1720.96 L846.865 1720.76 L846.583 1720.76 L846.583 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="846.583,1720.76 846.583,1720.96 846.865,1720.96 846.865,1720.76 846.583,1720.76 "/>
<path clip-path="url(#clip322)" d="M846.865 1720.17 L846.865 1720.96 L847.147 1720.96 L847.147 1720.17 L846.865 1720.17 L846.865 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="846.865,1720.17 846.865,1720.96 847.147,1720.96 847.147,1720.17 846.865,1720.17 "/>
<path clip-path="url(#clip322)" d="M847.147 1720.56 L847.147 1720.96 L847.428 1720.96 L847.428 1720.56 L847.147 1720.56 L847.147 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="847.147,1720.56 847.147,1720.96 847.428,1720.96 847.428,1720.56 847.147,1720.56 "/>
<path clip-path="url(#clip322)" d="M847.428 1719.97 L847.428 1720.96 L847.71 1720.96 L847.71 1719.97 L847.428 1719.97 L847.428 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="847.428,1719.97 847.428,1720.96 847.71,1720.96 847.71,1719.97 847.428,1719.97 "/>
<path clip-path="url(#clip322)" d="M847.71 1720.76 L847.71 1720.96 L847.992 1720.96 L847.992 1720.76 L847.71 1720.76 L847.71 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="847.71,1720.76 847.71,1720.96 847.992,1720.96 847.992,1720.76 847.71,1720.76 "/>
<path clip-path="url(#clip322)" d="M847.992 1720.17 L847.992 1720.96 L848.274 1720.96 L848.274 1720.17 L847.992 1720.17 L847.992 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="847.992,1720.17 847.992,1720.96 848.274,1720.96 848.274,1720.17 847.992,1720.17 "/>
<path clip-path="url(#clip322)" d="M848.274 1720.17 L848.274 1720.96 L848.555 1720.96 L848.555 1720.17 L848.274 1720.17 L848.274 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="848.274,1720.17 848.274,1720.96 848.555,1720.96 848.555,1720.17 848.274,1720.17 "/>
<path clip-path="url(#clip322)" d="M848.555 1720.56 L848.555 1720.96 L848.837 1720.96 L848.837 1720.56 L848.555 1720.56 L848.555 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="848.555,1720.56 848.555,1720.96 848.837,1720.96 848.837,1720.56 848.555,1720.56 "/>
<path clip-path="url(#clip322)" d="M848.837 1720.37 L848.837 1720.96 L849.119 1720.96 L849.119 1720.37 L848.837 1720.37 L848.837 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="848.837,1720.37 848.837,1720.96 849.119,1720.96 849.119,1720.37 848.837,1720.37 "/>
<path clip-path="url(#clip322)" d="M849.119 1720.37 L849.119 1720.96 L849.401 1720.96 L849.401 1720.37 L849.119 1720.37 L849.119 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="849.119,1720.37 849.119,1720.96 849.401,1720.96 849.401,1720.37 849.119,1720.37 "/>
<path clip-path="url(#clip322)" d="M849.401 1720.56 L849.401 1720.96 L849.682 1720.96 L849.682 1720.56 L849.401 1720.56 L849.401 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="849.401,1720.56 849.401,1720.96 849.682,1720.96 849.682,1720.56 849.401,1720.56 "/>
<path clip-path="url(#clip322)" d="M849.682 1719.97 L849.682 1720.96 L849.964 1720.96 L849.964 1719.97 L849.682 1719.97 L849.682 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="849.682,1719.97 849.682,1720.96 849.964,1720.96 849.964,1719.97 849.682,1719.97 "/>
<path clip-path="url(#clip322)" d="M849.964 1720.56 L849.964 1720.96 L850.246 1720.96 L850.246 1720.56 L849.964 1720.56 L849.964 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="849.964,1720.56 849.964,1720.96 850.246,1720.96 850.246,1720.56 849.964,1720.56 "/>
<path clip-path="url(#clip322)" d="M850.246 1720.56 L850.246 1720.96 L850.527 1720.96 L850.527 1720.56 L850.246 1720.56 L850.246 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="850.246,1720.56 850.246,1720.96 850.527,1720.96 850.527,1720.56 850.246,1720.56 "/>
<path clip-path="url(#clip322)" d="M850.527 1720.17 L850.527 1720.96 L850.809 1720.96 L850.809 1720.17 L850.527 1720.17 L850.527 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="850.527,1720.17 850.527,1720.96 850.809,1720.96 850.809,1720.17 850.527,1720.17 "/>
<path clip-path="url(#clip322)" d="M850.809 1720.37 L850.809 1720.96 L851.091 1720.96 L851.091 1720.37 L850.809 1720.37 L850.809 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="850.809,1720.37 850.809,1720.96 851.091,1720.96 851.091,1720.37 850.809,1720.37 "/>
<path clip-path="url(#clip322)" d="M851.091 1719.58 L851.091 1720.96 L851.373 1720.96 L851.373 1719.58 L851.091 1719.58 L851.091 1719.58  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="851.091,1719.58 851.091,1720.96 851.373,1720.96 851.373,1719.58 851.091,1719.58 "/>
<path clip-path="url(#clip322)" d="M851.373 1720.17 L851.373 1720.96 L851.654 1720.96 L851.654 1720.17 L851.373 1720.17 L851.373 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="851.373,1720.17 851.373,1720.96 851.654,1720.96 851.654,1720.17 851.373,1720.17 "/>
<path clip-path="url(#clip322)" d="M851.654 1720.76 L851.654 1720.96 L851.936 1720.96 L851.936 1720.76 L851.654 1720.76 L851.654 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="851.654,1720.76 851.654,1720.96 851.936,1720.96 851.936,1720.76 851.654,1720.76 "/>
<path clip-path="url(#clip322)" d="M851.936 1720.56 L851.936 1720.96 L852.218 1720.96 L852.218 1720.56 L851.936 1720.56 L851.936 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="851.936,1720.56 851.936,1720.96 852.218,1720.96 852.218,1720.56 851.936,1720.56 "/>
<path clip-path="url(#clip322)" d="M852.218 1720.17 L852.218 1720.96 L852.499 1720.96 L852.499 1720.17 L852.218 1720.17 L852.218 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="852.218,1720.17 852.218,1720.96 852.499,1720.96 852.499,1720.17 852.218,1720.17 "/>
<path clip-path="url(#clip322)" d="M852.499 1720.37 L852.499 1720.96 L852.781 1720.96 L852.781 1720.37 L852.499 1720.37 L852.499 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="852.499,1720.37 852.499,1720.96 852.781,1720.96 852.781,1720.37 852.499,1720.37 "/>
<path clip-path="url(#clip322)" d="M852.781 1720.96 L852.781 1720.96 L853.063 1720.96 L853.063 1720.96 L852.781 1720.96 L852.781 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="852.781,1720.96 852.781,1720.96 853.063,1720.96 852.781,1720.96 "/>
<path clip-path="url(#clip322)" d="M853.063 1720.76 L853.063 1720.96 L853.345 1720.96 L853.345 1720.76 L853.063 1720.76 L853.063 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="853.063,1720.76 853.063,1720.96 853.345,1720.96 853.345,1720.76 853.063,1720.76 "/>
<path clip-path="url(#clip322)" d="M853.345 1720.37 L853.345 1720.96 L853.626 1720.96 L853.626 1720.37 L853.345 1720.37 L853.345 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="853.345,1720.37 853.345,1720.96 853.626,1720.96 853.626,1720.37 853.345,1720.37 "/>
<path clip-path="url(#clip322)" d="M853.626 1719.78 L853.626 1720.96 L853.908 1720.96 L853.908 1719.78 L853.626 1719.78 L853.626 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="853.626,1719.78 853.626,1720.96 853.908,1720.96 853.908,1719.78 853.626,1719.78 "/>
<path clip-path="url(#clip322)" d="M853.908 1720.56 L853.908 1720.96 L854.19 1720.96 L854.19 1720.56 L853.908 1720.56 L853.908 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="853.908,1720.56 853.908,1720.96 854.19,1720.96 854.19,1720.56 853.908,1720.56 "/>
<path clip-path="url(#clip322)" d="M854.19 1720.76 L854.19 1720.96 L854.472 1720.96 L854.472 1720.76 L854.19 1720.76 L854.19 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="854.19,1720.76 854.19,1720.96 854.472,1720.96 854.472,1720.76 854.19,1720.76 "/>
<path clip-path="url(#clip322)" d="M854.472 1720.37 L854.472 1720.96 L854.753 1720.96 L854.753 1720.37 L854.472 1720.37 L854.472 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="854.472,1720.37 854.472,1720.96 854.753,1720.96 854.753,1720.37 854.472,1720.37 "/>
<path clip-path="url(#clip322)" d="M854.753 1720.37 L854.753 1720.96 L855.035 1720.96 L855.035 1720.37 L854.753 1720.37 L854.753 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="854.753,1720.37 854.753,1720.96 855.035,1720.96 855.035,1720.37 854.753,1720.37 "/>
<path clip-path="url(#clip322)" d="M855.035 1720.56 L855.035 1720.96 L855.317 1720.96 L855.317 1720.56 L855.035 1720.56 L855.035 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="855.035,1720.56 855.035,1720.96 855.317,1720.96 855.317,1720.56 855.035,1720.56 "/>
<path clip-path="url(#clip322)" d="M855.317 1720.17 L855.317 1720.96 L855.598 1720.96 L855.598 1720.17 L855.317 1720.17 L855.317 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="855.317,1720.17 855.317,1720.96 855.598,1720.96 855.598,1720.17 855.317,1720.17 "/>
<path clip-path="url(#clip322)" d="M855.598 1719.97 L855.598 1720.96 L855.88 1720.96 L855.88 1719.97 L855.598 1719.97 L855.598 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="855.598,1719.97 855.598,1720.96 855.88,1720.96 855.88,1719.97 855.598,1719.97 "/>
<path clip-path="url(#clip322)" d="M855.88 1720.37 L855.88 1720.96 L856.162 1720.96 L856.162 1720.37 L855.88 1720.37 L855.88 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="855.88,1720.37 855.88,1720.96 856.162,1720.96 856.162,1720.37 855.88,1720.37 "/>
<path clip-path="url(#clip322)" d="M856.162 1720.17 L856.162 1720.96 L856.444 1720.96 L856.444 1720.17 L856.162 1720.17 L856.162 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="856.162,1720.17 856.162,1720.96 856.444,1720.96 856.444,1720.17 856.162,1720.17 "/>
<path clip-path="url(#clip322)" d="M856.444 1720.56 L856.444 1720.96 L856.725 1720.96 L856.725 1720.56 L856.444 1720.56 L856.444 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="856.444,1720.56 856.444,1720.96 856.725,1720.96 856.725,1720.56 856.444,1720.56 "/>
<path clip-path="url(#clip322)" d="M856.725 1719.97 L856.725 1720.96 L857.007 1720.96 L857.007 1719.97 L856.725 1719.97 L856.725 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="856.725,1719.97 856.725,1720.96 857.007,1720.96 857.007,1719.97 856.725,1719.97 "/>
<path clip-path="url(#clip322)" d="M857.007 1720.56 L857.007 1720.96 L857.289 1720.96 L857.289 1720.56 L857.007 1720.56 L857.007 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="857.007,1720.56 857.007,1720.96 857.289,1720.96 857.289,1720.56 857.007,1720.56 "/>
<path clip-path="url(#clip322)" d="M857.289 1720.76 L857.289 1720.96 L857.571 1720.96 L857.571 1720.76 L857.289 1720.76 L857.289 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="857.289,1720.76 857.289,1720.96 857.571,1720.96 857.571,1720.76 857.289,1720.76 "/>
<path clip-path="url(#clip322)" d="M857.571 1719.97 L857.571 1720.96 L857.852 1720.96 L857.852 1719.97 L857.571 1719.97 L857.571 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="857.571,1719.97 857.571,1720.96 857.852,1720.96 857.852,1719.97 857.571,1719.97 "/>
<path clip-path="url(#clip322)" d="M857.852 1720.76 L857.852 1720.96 L858.134 1720.96 L858.134 1720.76 L857.852 1720.76 L857.852 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="857.852,1720.76 857.852,1720.96 858.134,1720.96 858.134,1720.76 857.852,1720.76 "/>
<path clip-path="url(#clip322)" d="M858.134 1720.17 L858.134 1720.96 L858.416 1720.96 L858.416 1720.17 L858.134 1720.17 L858.134 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="858.134,1720.17 858.134,1720.96 858.416,1720.96 858.416,1720.17 858.134,1720.17 "/>
<path clip-path="url(#clip322)" d="M858.416 1720.96 L858.416 1720.96 L858.697 1720.96 L858.697 1720.96 L858.416 1720.96 L858.416 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="858.416,1720.96 858.416,1720.96 858.697,1720.96 858.416,1720.96 "/>
<path clip-path="url(#clip322)" d="M858.697 1720.17 L858.697 1720.96 L858.979 1720.96 L858.979 1720.17 L858.697 1720.17 L858.697 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="858.697,1720.17 858.697,1720.96 858.979,1720.96 858.979,1720.17 858.697,1720.17 "/>
<path clip-path="url(#clip322)" d="M858.979 1720.37 L858.979 1720.96 L859.261 1720.96 L859.261 1720.37 L858.979 1720.37 L858.979 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="858.979,1720.37 858.979,1720.96 859.261,1720.96 859.261,1720.37 858.979,1720.37 "/>
<path clip-path="url(#clip322)" d="M859.261 1720.17 L859.261 1720.96 L859.543 1720.96 L859.543 1720.17 L859.261 1720.17 L859.261 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="859.261,1720.17 859.261,1720.96 859.543,1720.96 859.543,1720.17 859.261,1720.17 "/>
<path clip-path="url(#clip322)" d="M859.543 1720.76 L859.543 1720.96 L859.824 1720.96 L859.824 1720.76 L859.543 1720.76 L859.543 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="859.543,1720.76 859.543,1720.96 859.824,1720.96 859.824,1720.76 859.543,1720.76 "/>
<path clip-path="url(#clip322)" d="M859.824 1720.37 L859.824 1720.96 L860.106 1720.96 L860.106 1720.37 L859.824 1720.37 L859.824 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="859.824,1720.37 859.824,1720.96 860.106,1720.96 860.106,1720.37 859.824,1720.37 "/>
<path clip-path="url(#clip322)" d="M860.106 1720.76 L860.106 1720.96 L860.388 1720.96 L860.388 1720.76 L860.106 1720.76 L860.106 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="860.106,1720.76 860.106,1720.96 860.388,1720.96 860.388,1720.76 860.106,1720.76 "/>
<path clip-path="url(#clip322)" d="M860.388 1720.56 L860.388 1720.96 L860.67 1720.96 L860.67 1720.56 L860.388 1720.56 L860.388 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="860.388,1720.56 860.388,1720.96 860.67,1720.96 860.67,1720.56 860.388,1720.56 "/>
<path clip-path="url(#clip322)" d="M860.67 1720.17 L860.67 1720.96 L860.951 1720.96 L860.951 1720.17 L860.67 1720.17 L860.67 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="860.67,1720.17 860.67,1720.96 860.951,1720.96 860.951,1720.17 860.67,1720.17 "/>
<path clip-path="url(#clip322)" d="M860.951 1720.37 L860.951 1720.96 L861.233 1720.96 L861.233 1720.37 L860.951 1720.37 L860.951 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="860.951,1720.37 860.951,1720.96 861.233,1720.96 861.233,1720.37 860.951,1720.37 "/>
<path clip-path="url(#clip322)" d="M861.233 1720.56 L861.233 1720.96 L861.515 1720.96 L861.515 1720.56 L861.233 1720.56 L861.233 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="861.233,1720.56 861.233,1720.96 861.515,1720.96 861.515,1720.56 861.233,1720.56 "/>
<path clip-path="url(#clip322)" d="M861.515 1720.37 L861.515 1720.96 L861.796 1720.96 L861.796 1720.37 L861.515 1720.37 L861.515 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="861.515,1720.37 861.515,1720.96 861.796,1720.96 861.796,1720.37 861.515,1720.37 "/>
<path clip-path="url(#clip322)" d="M861.796 1720.76 L861.796 1720.96 L862.078 1720.96 L862.078 1720.76 L861.796 1720.76 L861.796 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="861.796,1720.76 861.796,1720.96 862.078,1720.96 862.078,1720.76 861.796,1720.76 "/>
<path clip-path="url(#clip322)" d="M862.078 1720.76 L862.078 1720.96 L862.36 1720.96 L862.36 1720.76 L862.078 1720.76 L862.078 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="862.078,1720.76 862.078,1720.96 862.36,1720.96 862.36,1720.76 862.078,1720.76 "/>
<path clip-path="url(#clip322)" d="M862.36 1720.37 L862.36 1720.96 L862.642 1720.96 L862.642 1720.37 L862.36 1720.37 L862.36 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="862.36,1720.37 862.36,1720.96 862.642,1720.96 862.642,1720.37 862.36,1720.37 "/>
<path clip-path="url(#clip322)" d="M862.642 1720.76 L862.642 1720.96 L862.923 1720.96 L862.923 1720.76 L862.642 1720.76 L862.642 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="862.642,1720.76 862.642,1720.96 862.923,1720.96 862.923,1720.76 862.642,1720.76 "/>
<path clip-path="url(#clip322)" d="M862.923 1720.56 L862.923 1720.96 L863.205 1720.96 L863.205 1720.56 L862.923 1720.56 L862.923 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="862.923,1720.56 862.923,1720.96 863.205,1720.96 863.205,1720.56 862.923,1720.56 "/>
<path clip-path="url(#clip322)" d="M863.205 1720.76 L863.205 1720.96 L863.487 1720.96 L863.487 1720.76 L863.205 1720.76 L863.205 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="863.205,1720.76 863.205,1720.96 863.487,1720.96 863.487,1720.76 863.205,1720.76 "/>
<path clip-path="url(#clip322)" d="M863.487 1720.76 L863.487 1720.96 L863.769 1720.96 L863.769 1720.76 L863.487 1720.76 L863.487 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="863.487,1720.76 863.487,1720.96 863.769,1720.96 863.769,1720.76 863.487,1720.76 "/>
<path clip-path="url(#clip322)" d="M863.769 1720.37 L863.769 1720.96 L864.05 1720.96 L864.05 1720.37 L863.769 1720.37 L863.769 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="863.769,1720.37 863.769,1720.96 864.05,1720.96 864.05,1720.37 863.769,1720.37 "/>
<path clip-path="url(#clip322)" d="M864.05 1720.37 L864.05 1720.96 L864.332 1720.96 L864.332 1720.37 L864.05 1720.37 L864.05 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="864.05,1720.37 864.05,1720.96 864.332,1720.96 864.332,1720.37 864.05,1720.37 "/>
<path clip-path="url(#clip322)" d="M864.332 1719.97 L864.332 1720.96 L864.614 1720.96 L864.614 1719.97 L864.332 1719.97 L864.332 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="864.332,1719.97 864.332,1720.96 864.614,1720.96 864.614,1719.97 864.332,1719.97 "/>
<path clip-path="url(#clip322)" d="M864.614 1720.17 L864.614 1720.96 L864.895 1720.96 L864.895 1720.17 L864.614 1720.17 L864.614 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="864.614,1720.17 864.614,1720.96 864.895,1720.96 864.895,1720.17 864.614,1720.17 "/>
<path clip-path="url(#clip322)" d="M864.895 1720.37 L864.895 1720.96 L865.177 1720.96 L865.177 1720.37 L864.895 1720.37 L864.895 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="864.895,1720.37 864.895,1720.96 865.177,1720.96 865.177,1720.37 864.895,1720.37 "/>
<path clip-path="url(#clip322)" d="M865.177 1720.56 L865.177 1720.96 L865.459 1720.96 L865.459 1720.56 L865.177 1720.56 L865.177 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="865.177,1720.56 865.177,1720.96 865.459,1720.96 865.459,1720.56 865.177,1720.56 "/>
<path clip-path="url(#clip322)" d="M865.459 1720.76 L865.459 1720.96 L865.741 1720.96 L865.741 1720.76 L865.459 1720.76 L865.459 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="865.459,1720.76 865.459,1720.96 865.741,1720.96 865.741,1720.76 865.459,1720.76 "/>
<path clip-path="url(#clip322)" d="M865.741 1720.76 L865.741 1720.96 L866.022 1720.96 L866.022 1720.76 L865.741 1720.76 L865.741 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="865.741,1720.76 865.741,1720.96 866.022,1720.96 866.022,1720.76 865.741,1720.76 "/>
<path clip-path="url(#clip322)" d="M866.022 1720.56 L866.022 1720.96 L866.304 1720.96 L866.304 1720.56 L866.022 1720.56 L866.022 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="866.022,1720.56 866.022,1720.96 866.304,1720.96 866.304,1720.56 866.022,1720.56 "/>
<path clip-path="url(#clip322)" d="M866.304 1720.37 L866.304 1720.96 L866.586 1720.96 L866.586 1720.37 L866.304 1720.37 L866.304 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="866.304,1720.37 866.304,1720.96 866.586,1720.96 866.586,1720.37 866.304,1720.37 "/>
<path clip-path="url(#clip322)" d="M866.586 1719.97 L866.586 1720.96 L866.867 1720.96 L866.867 1719.97 L866.586 1719.97 L866.586 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="866.586,1719.97 866.586,1720.96 866.867,1720.96 866.867,1719.97 866.586,1719.97 "/>
<path clip-path="url(#clip322)" d="M866.867 1720.56 L866.867 1720.96 L867.149 1720.96 L867.149 1720.56 L866.867 1720.56 L866.867 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="866.867,1720.56 866.867,1720.96 867.149,1720.96 867.149,1720.56 866.867,1720.56 "/>
<path clip-path="url(#clip322)" d="M867.149 1720.37 L867.149 1720.96 L867.431 1720.96 L867.431 1720.37 L867.149 1720.37 L867.149 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="867.149,1720.37 867.149,1720.96 867.431,1720.96 867.431,1720.37 867.149,1720.37 "/>
<path clip-path="url(#clip322)" d="M867.431 1720.37 L867.431 1720.96 L867.713 1720.96 L867.713 1720.37 L867.431 1720.37 L867.431 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="867.431,1720.37 867.431,1720.96 867.713,1720.96 867.713,1720.37 867.431,1720.37 "/>
<path clip-path="url(#clip322)" d="M867.713 1720.56 L867.713 1720.96 L867.994 1720.96 L867.994 1720.56 L867.713 1720.56 L867.713 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="867.713,1720.56 867.713,1720.96 867.994,1720.96 867.994,1720.56 867.713,1720.56 "/>
<path clip-path="url(#clip322)" d="M867.994 1720.76 L867.994 1720.96 L868.276 1720.96 L868.276 1720.76 L867.994 1720.76 L867.994 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="867.994,1720.76 867.994,1720.96 868.276,1720.96 868.276,1720.76 867.994,1720.76 "/>
<path clip-path="url(#clip322)" d="M868.276 1720.76 L868.276 1720.96 L868.558 1720.96 L868.558 1720.76 L868.276 1720.76 L868.276 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="868.276,1720.76 868.276,1720.96 868.558,1720.96 868.558,1720.76 868.276,1720.76 "/>
<path clip-path="url(#clip322)" d="M868.558 1720.17 L868.558 1720.96 L868.84 1720.96 L868.84 1720.17 L868.558 1720.17 L868.558 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="868.558,1720.17 868.558,1720.96 868.84,1720.96 868.84,1720.17 868.558,1720.17 "/>
<path clip-path="url(#clip322)" d="M868.84 1720.96 L868.84 1720.96 L869.121 1720.96 L869.121 1720.96 L868.84 1720.96 L868.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="868.84,1720.96 868.84,1720.96 869.121,1720.96 868.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M869.121 1719.78 L869.121 1720.96 L869.403 1720.96 L869.403 1719.78 L869.121 1719.78 L869.121 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="869.121,1719.78 869.121,1720.96 869.403,1720.96 869.403,1719.78 869.121,1719.78 "/>
<path clip-path="url(#clip322)" d="M869.403 1720.56 L869.403 1720.96 L869.685 1720.96 L869.685 1720.56 L869.403 1720.56 L869.403 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="869.403,1720.56 869.403,1720.96 869.685,1720.96 869.685,1720.56 869.403,1720.56 "/>
<path clip-path="url(#clip322)" d="M869.685 1720.56 L869.685 1720.96 L869.966 1720.96 L869.966 1720.56 L869.685 1720.56 L869.685 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="869.685,1720.56 869.685,1720.96 869.966,1720.96 869.966,1720.56 869.685,1720.56 "/>
<path clip-path="url(#clip322)" d="M869.966 1720.76 L869.966 1720.96 L870.248 1720.96 L870.248 1720.76 L869.966 1720.76 L869.966 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="869.966,1720.76 869.966,1720.96 870.248,1720.96 870.248,1720.76 869.966,1720.76 "/>
<path clip-path="url(#clip322)" d="M870.248 1720.17 L870.248 1720.96 L870.53 1720.96 L870.53 1720.17 L870.248 1720.17 L870.248 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="870.248,1720.17 870.248,1720.96 870.53,1720.96 870.53,1720.17 870.248,1720.17 "/>
<path clip-path="url(#clip322)" d="M870.53 1720.76 L870.53 1720.96 L870.812 1720.96 L870.812 1720.76 L870.53 1720.76 L870.53 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="870.53,1720.76 870.53,1720.96 870.812,1720.96 870.812,1720.76 870.53,1720.76 "/>
<path clip-path="url(#clip322)" d="M870.812 1720.96 L870.812 1720.96 L871.093 1720.96 L871.093 1720.96 L870.812 1720.96 L870.812 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="870.812,1720.96 870.812,1720.96 871.093,1720.96 870.812,1720.96 "/>
<path clip-path="url(#clip322)" d="M871.093 1720.37 L871.093 1720.96 L871.375 1720.96 L871.375 1720.37 L871.093 1720.37 L871.093 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="871.093,1720.37 871.093,1720.96 871.375,1720.96 871.375,1720.37 871.093,1720.37 "/>
<path clip-path="url(#clip322)" d="M871.375 1720.56 L871.375 1720.96 L871.657 1720.96 L871.657 1720.56 L871.375 1720.56 L871.375 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="871.375,1720.56 871.375,1720.96 871.657,1720.96 871.657,1720.56 871.375,1720.56 "/>
<path clip-path="url(#clip322)" d="M871.657 1720.76 L871.657 1720.96 L871.939 1720.96 L871.939 1720.76 L871.657 1720.76 L871.657 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="871.657,1720.76 871.657,1720.96 871.939,1720.96 871.939,1720.76 871.657,1720.76 "/>
<path clip-path="url(#clip322)" d="M871.939 1720.56 L871.939 1720.96 L872.22 1720.96 L872.22 1720.56 L871.939 1720.56 L871.939 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="871.939,1720.56 871.939,1720.96 872.22,1720.96 872.22,1720.56 871.939,1720.56 "/>
<path clip-path="url(#clip322)" d="M872.22 1719.97 L872.22 1720.96 L872.502 1720.96 L872.502 1719.97 L872.22 1719.97 L872.22 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="872.22,1719.97 872.22,1720.96 872.502,1720.96 872.502,1719.97 872.22,1719.97 "/>
<path clip-path="url(#clip322)" d="M872.502 1720.56 L872.502 1720.96 L872.784 1720.96 L872.784 1720.56 L872.502 1720.56 L872.502 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="872.502,1720.56 872.502,1720.96 872.784,1720.96 872.784,1720.56 872.502,1720.56 "/>
<path clip-path="url(#clip322)" d="M872.784 1720.76 L872.784 1720.96 L873.065 1720.96 L873.065 1720.76 L872.784 1720.76 L872.784 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="872.784,1720.76 872.784,1720.96 873.065,1720.96 873.065,1720.76 872.784,1720.76 "/>
<path clip-path="url(#clip322)" d="M873.065 1720.56 L873.065 1720.96 L873.347 1720.96 L873.347 1720.56 L873.065 1720.56 L873.065 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="873.065,1720.56 873.065,1720.96 873.347,1720.96 873.347,1720.56 873.065,1720.56 "/>
<path clip-path="url(#clip322)" d="M873.347 1720.96 L873.347 1720.96 L873.629 1720.96 L873.629 1720.96 L873.347 1720.96 L873.347 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="873.347,1720.96 873.347,1720.96 873.629,1720.96 873.347,1720.96 "/>
<path clip-path="url(#clip322)" d="M873.629 1720.17 L873.629 1720.96 L873.911 1720.96 L873.911 1720.17 L873.629 1720.17 L873.629 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="873.629,1720.17 873.629,1720.96 873.911,1720.96 873.911,1720.17 873.629,1720.17 "/>
<path clip-path="url(#clip322)" d="M873.911 1720.37 L873.911 1720.96 L874.192 1720.96 L874.192 1720.37 L873.911 1720.37 L873.911 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="873.911,1720.37 873.911,1720.96 874.192,1720.96 874.192,1720.37 873.911,1720.37 "/>
<path clip-path="url(#clip322)" d="M874.192 1720.76 L874.192 1720.96 L874.474 1720.96 L874.474 1720.76 L874.192 1720.76 L874.192 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="874.192,1720.76 874.192,1720.96 874.474,1720.96 874.474,1720.76 874.192,1720.76 "/>
<path clip-path="url(#clip322)" d="M874.474 1720.56 L874.474 1720.96 L874.756 1720.96 L874.756 1720.56 L874.474 1720.56 L874.474 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="874.474,1720.56 874.474,1720.96 874.756,1720.96 874.756,1720.56 874.474,1720.56 "/>
<path clip-path="url(#clip322)" d="M874.756 1720.56 L874.756 1720.96 L875.038 1720.96 L875.038 1720.56 L874.756 1720.56 L874.756 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="874.756,1720.56 874.756,1720.96 875.038,1720.96 875.038,1720.56 874.756,1720.56 "/>
<path clip-path="url(#clip322)" d="M875.038 1720.56 L875.038 1720.96 L875.319 1720.96 L875.319 1720.56 L875.038 1720.56 L875.038 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="875.038,1720.56 875.038,1720.96 875.319,1720.96 875.319,1720.56 875.038,1720.56 "/>
<path clip-path="url(#clip322)" d="M875.319 1720.37 L875.319 1720.96 L875.601 1720.96 L875.601 1720.37 L875.319 1720.37 L875.319 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="875.319,1720.37 875.319,1720.96 875.601,1720.96 875.601,1720.37 875.319,1720.37 "/>
<path clip-path="url(#clip322)" d="M875.601 1720.17 L875.601 1720.96 L875.883 1720.96 L875.883 1720.17 L875.601 1720.17 L875.601 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="875.601,1720.17 875.601,1720.96 875.883,1720.96 875.883,1720.17 875.601,1720.17 "/>
<path clip-path="url(#clip322)" d="M875.883 1720.37 L875.883 1720.96 L876.164 1720.96 L876.164 1720.37 L875.883 1720.37 L875.883 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="875.883,1720.37 875.883,1720.96 876.164,1720.96 876.164,1720.37 875.883,1720.37 "/>
<path clip-path="url(#clip322)" d="M876.164 1720.56 L876.164 1720.96 L876.446 1720.96 L876.446 1720.56 L876.164 1720.56 L876.164 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="876.164,1720.56 876.164,1720.96 876.446,1720.96 876.446,1720.56 876.164,1720.56 "/>
<path clip-path="url(#clip322)" d="M876.446 1720.76 L876.446 1720.96 L876.728 1720.96 L876.728 1720.76 L876.446 1720.76 L876.446 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="876.446,1720.76 876.446,1720.96 876.728,1720.96 876.728,1720.76 876.446,1720.76 "/>
<path clip-path="url(#clip322)" d="M876.728 1720.56 L876.728 1720.96 L877.01 1720.96 L877.01 1720.56 L876.728 1720.56 L876.728 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="876.728,1720.56 876.728,1720.96 877.01,1720.96 877.01,1720.56 876.728,1720.56 "/>
<path clip-path="url(#clip322)" d="M877.01 1719.78 L877.01 1720.96 L877.291 1720.96 L877.291 1719.78 L877.01 1719.78 L877.01 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="877.01,1719.78 877.01,1720.96 877.291,1720.96 877.291,1719.78 877.01,1719.78 "/>
<path clip-path="url(#clip322)" d="M877.291 1720.96 L877.291 1720.96 L877.573 1720.96 L877.573 1720.96 L877.291 1720.96 L877.291 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="877.291,1720.96 877.291,1720.96 877.573,1720.96 877.291,1720.96 "/>
<path clip-path="url(#clip322)" d="M877.573 1720.56 L877.573 1720.96 L877.855 1720.96 L877.855 1720.56 L877.573 1720.56 L877.573 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="877.573,1720.56 877.573,1720.96 877.855,1720.96 877.855,1720.56 877.573,1720.56 "/>
<path clip-path="url(#clip322)" d="M877.855 1720.56 L877.855 1720.96 L878.137 1720.96 L878.137 1720.56 L877.855 1720.56 L877.855 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="877.855,1720.56 877.855,1720.96 878.137,1720.96 878.137,1720.56 877.855,1720.56 "/>
<path clip-path="url(#clip322)" d="M878.137 1720.56 L878.137 1720.96 L878.418 1720.96 L878.418 1720.56 L878.137 1720.56 L878.137 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="878.137,1720.56 878.137,1720.96 878.418,1720.96 878.418,1720.56 878.137,1720.56 "/>
<path clip-path="url(#clip322)" d="M878.418 1719.97 L878.418 1720.96 L878.7 1720.96 L878.7 1719.97 L878.418 1719.97 L878.418 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="878.418,1719.97 878.418,1720.96 878.7,1720.96 878.7,1719.97 878.418,1719.97 "/>
<path clip-path="url(#clip322)" d="M878.7 1719.97 L878.7 1720.96 L878.982 1720.96 L878.982 1719.97 L878.7 1719.97 L878.7 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="878.7,1719.97 878.7,1720.96 878.982,1720.96 878.982,1719.97 878.7,1719.97 "/>
<path clip-path="url(#clip322)" d="M878.982 1719.97 L878.982 1720.96 L879.263 1720.96 L879.263 1719.97 L878.982 1719.97 L878.982 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="878.982,1719.97 878.982,1720.96 879.263,1720.96 879.263,1719.97 878.982,1719.97 "/>
<path clip-path="url(#clip322)" d="M879.263 1720.17 L879.263 1720.96 L879.545 1720.96 L879.545 1720.17 L879.263 1720.17 L879.263 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="879.263,1720.17 879.263,1720.96 879.545,1720.96 879.545,1720.17 879.263,1720.17 "/>
<path clip-path="url(#clip322)" d="M879.545 1720.56 L879.545 1720.96 L879.827 1720.96 L879.827 1720.56 L879.545 1720.56 L879.545 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="879.545,1720.56 879.545,1720.96 879.827,1720.96 879.827,1720.56 879.545,1720.56 "/>
<path clip-path="url(#clip322)" d="M879.827 1720.37 L879.827 1720.96 L880.109 1720.96 L880.109 1720.37 L879.827 1720.37 L879.827 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="879.827,1720.37 879.827,1720.96 880.109,1720.96 880.109,1720.37 879.827,1720.37 "/>
<path clip-path="url(#clip322)" d="M880.109 1720.56 L880.109 1720.96 L880.39 1720.96 L880.39 1720.56 L880.109 1720.56 L880.109 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="880.109,1720.56 880.109,1720.96 880.39,1720.96 880.39,1720.56 880.109,1720.56 "/>
<path clip-path="url(#clip322)" d="M880.39 1720.37 L880.39 1720.96 L880.672 1720.96 L880.672 1720.37 L880.39 1720.37 L880.39 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="880.39,1720.37 880.39,1720.96 880.672,1720.96 880.672,1720.37 880.39,1720.37 "/>
<path clip-path="url(#clip322)" d="M880.672 1720.56 L880.672 1720.96 L880.954 1720.96 L880.954 1720.56 L880.672 1720.56 L880.672 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="880.672,1720.56 880.672,1720.96 880.954,1720.96 880.954,1720.56 880.672,1720.56 "/>
<path clip-path="url(#clip322)" d="M880.954 1720.37 L880.954 1720.96 L881.236 1720.96 L881.236 1720.37 L880.954 1720.37 L880.954 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="880.954,1720.37 880.954,1720.96 881.236,1720.96 881.236,1720.37 880.954,1720.37 "/>
<path clip-path="url(#clip322)" d="M881.236 1720.76 L881.236 1720.96 L881.517 1720.96 L881.517 1720.76 L881.236 1720.76 L881.236 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="881.236,1720.76 881.236,1720.96 881.517,1720.96 881.517,1720.76 881.236,1720.76 "/>
<path clip-path="url(#clip322)" d="M881.517 1720.17 L881.517 1720.96 L881.799 1720.96 L881.799 1720.17 L881.517 1720.17 L881.517 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="881.517,1720.17 881.517,1720.96 881.799,1720.96 881.799,1720.17 881.517,1720.17 "/>
<path clip-path="url(#clip322)" d="M881.799 1719.97 L881.799 1720.96 L882.081 1720.96 L882.081 1719.97 L881.799 1719.97 L881.799 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="881.799,1719.97 881.799,1720.96 882.081,1720.96 882.081,1719.97 881.799,1719.97 "/>
<path clip-path="url(#clip322)" d="M882.081 1720.37 L882.081 1720.96 L882.362 1720.96 L882.362 1720.37 L882.081 1720.37 L882.081 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="882.081,1720.37 882.081,1720.96 882.362,1720.96 882.362,1720.37 882.081,1720.37 "/>
<path clip-path="url(#clip322)" d="M882.362 1720.76 L882.362 1720.96 L882.644 1720.96 L882.644 1720.76 L882.362 1720.76 L882.362 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="882.362,1720.76 882.362,1720.96 882.644,1720.96 882.644,1720.76 882.362,1720.76 "/>
<path clip-path="url(#clip322)" d="M882.644 1720.56 L882.644 1720.96 L882.926 1720.96 L882.926 1720.56 L882.644 1720.56 L882.644 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="882.644,1720.56 882.644,1720.96 882.926,1720.96 882.926,1720.56 882.644,1720.56 "/>
<path clip-path="url(#clip322)" d="M882.926 1719.78 L882.926 1720.96 L883.208 1720.96 L883.208 1719.78 L882.926 1719.78 L882.926 1719.78  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="882.926,1719.78 882.926,1720.96 883.208,1720.96 883.208,1719.78 882.926,1719.78 "/>
<path clip-path="url(#clip322)" d="M883.208 1720.76 L883.208 1720.96 L883.489 1720.96 L883.489 1720.76 L883.208 1720.76 L883.208 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="883.208,1720.76 883.208,1720.96 883.489,1720.96 883.489,1720.76 883.208,1720.76 "/>
<path clip-path="url(#clip322)" d="M883.489 1720.76 L883.489 1720.96 L883.771 1720.96 L883.771 1720.76 L883.489 1720.76 L883.489 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="883.489,1720.76 883.489,1720.96 883.771,1720.96 883.771,1720.76 883.489,1720.76 "/>
<path clip-path="url(#clip322)" d="M883.771 1720.76 L883.771 1720.96 L884.053 1720.96 L884.053 1720.76 L883.771 1720.76 L883.771 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="883.771,1720.76 883.771,1720.96 884.053,1720.96 884.053,1720.76 883.771,1720.76 "/>
<path clip-path="url(#clip322)" d="M884.053 1720.56 L884.053 1720.96 L884.334 1720.96 L884.334 1720.56 L884.053 1720.56 L884.053 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="884.053,1720.56 884.053,1720.96 884.334,1720.96 884.334,1720.56 884.053,1720.56 "/>
<path clip-path="url(#clip322)" d="M884.334 1720.56 L884.334 1720.96 L884.616 1720.96 L884.616 1720.56 L884.334 1720.56 L884.334 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="884.334,1720.56 884.334,1720.96 884.616,1720.96 884.616,1720.56 884.334,1720.56 "/>
<path clip-path="url(#clip322)" d="M884.616 1720.96 L884.616 1720.96 L884.898 1720.96 L884.898 1720.96 L884.616 1720.96 L884.616 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="884.616,1720.96 884.616,1720.96 884.898,1720.96 884.616,1720.96 "/>
<path clip-path="url(#clip322)" d="M884.898 1720.56 L884.898 1720.96 L885.18 1720.96 L885.18 1720.56 L884.898 1720.56 L884.898 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="884.898,1720.56 884.898,1720.96 885.18,1720.96 885.18,1720.56 884.898,1720.56 "/>
<path clip-path="url(#clip322)" d="M885.18 1720.56 L885.18 1720.96 L885.461 1720.96 L885.461 1720.56 L885.18 1720.56 L885.18 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="885.18,1720.56 885.18,1720.96 885.461,1720.96 885.461,1720.56 885.18,1720.56 "/>
<path clip-path="url(#clip322)" d="M885.461 1720.56 L885.461 1720.96 L885.743 1720.96 L885.743 1720.56 L885.461 1720.56 L885.461 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="885.461,1720.56 885.461,1720.96 885.743,1720.96 885.743,1720.56 885.461,1720.56 "/>
<path clip-path="url(#clip322)" d="M885.743 1720.56 L885.743 1720.96 L886.025 1720.96 L886.025 1720.56 L885.743 1720.56 L885.743 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="885.743,1720.56 885.743,1720.96 886.025,1720.96 886.025,1720.56 885.743,1720.56 "/>
<path clip-path="url(#clip322)" d="M886.025 1719.38 L886.025 1720.96 L886.307 1720.96 L886.307 1719.38 L886.025 1719.38 L886.025 1719.38  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="886.025,1719.38 886.025,1720.96 886.307,1720.96 886.307,1719.38 886.025,1719.38 "/>
<path clip-path="url(#clip322)" d="M886.307 1720.96 L886.307 1720.96 L886.588 1720.96 L886.588 1720.96 L886.307 1720.96 L886.307 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="886.307,1720.96 886.307,1720.96 886.588,1720.96 886.307,1720.96 "/>
<path clip-path="url(#clip322)" d="M886.588 1720.76 L886.588 1720.96 L886.87 1720.96 L886.87 1720.76 L886.588 1720.76 L886.588 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="886.588,1720.76 886.588,1720.96 886.87,1720.96 886.87,1720.76 886.588,1720.76 "/>
<path clip-path="url(#clip322)" d="M886.87 1720.96 L886.87 1720.96 L887.152 1720.96 L887.152 1720.96 L886.87 1720.96 L886.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="886.87,1720.96 886.87,1720.96 887.152,1720.96 886.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M887.152 1720.37 L887.152 1720.96 L887.433 1720.96 L887.433 1720.37 L887.152 1720.37 L887.152 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="887.152,1720.37 887.152,1720.96 887.433,1720.96 887.433,1720.37 887.152,1720.37 "/>
<path clip-path="url(#clip322)" d="M887.433 1720.56 L887.433 1720.96 L887.715 1720.96 L887.715 1720.56 L887.433 1720.56 L887.433 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="887.433,1720.56 887.433,1720.96 887.715,1720.96 887.715,1720.56 887.433,1720.56 "/>
<path clip-path="url(#clip322)" d="M887.715 1720.96 L887.715 1720.96 L887.997 1720.96 L887.997 1720.96 L887.715 1720.96 L887.715 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="887.715,1720.96 887.715,1720.96 887.997,1720.96 887.715,1720.96 "/>
<path clip-path="url(#clip322)" d="M887.997 1720.96 L887.997 1720.96 L888.279 1720.96 L888.279 1720.96 L887.997 1720.96 L887.997 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="887.997,1720.96 887.997,1720.96 888.279,1720.96 887.997,1720.96 "/>
<path clip-path="url(#clip322)" d="M888.279 1720.56 L888.279 1720.96 L888.56 1720.96 L888.56 1720.56 L888.279 1720.56 L888.279 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="888.279,1720.56 888.279,1720.96 888.56,1720.96 888.56,1720.56 888.279,1720.56 "/>
<path clip-path="url(#clip322)" d="M888.56 1720.76 L888.56 1720.96 L888.842 1720.96 L888.842 1720.76 L888.56 1720.76 L888.56 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="888.56,1720.76 888.56,1720.96 888.842,1720.96 888.842,1720.76 888.56,1720.76 "/>
<path clip-path="url(#clip322)" d="M888.842 1720.76 L888.842 1720.96 L889.124 1720.96 L889.124 1720.76 L888.842 1720.76 L888.842 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="888.842,1720.76 888.842,1720.96 889.124,1720.96 889.124,1720.76 888.842,1720.76 "/>
<path clip-path="url(#clip322)" d="M889.124 1720.37 L889.124 1720.96 L889.406 1720.96 L889.406 1720.37 L889.124 1720.37 L889.124 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="889.124,1720.37 889.124,1720.96 889.406,1720.96 889.406,1720.37 889.124,1720.37 "/>
<path clip-path="url(#clip322)" d="M889.406 1720.76 L889.406 1720.96 L889.687 1720.96 L889.687 1720.76 L889.406 1720.76 L889.406 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="889.406,1720.76 889.406,1720.96 889.687,1720.96 889.687,1720.76 889.406,1720.76 "/>
<path clip-path="url(#clip322)" d="M889.687 1720.37 L889.687 1720.96 L889.969 1720.96 L889.969 1720.37 L889.687 1720.37 L889.687 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="889.687,1720.37 889.687,1720.96 889.969,1720.96 889.969,1720.37 889.687,1720.37 "/>
<path clip-path="url(#clip322)" d="M889.969 1720.96 L889.969 1720.96 L890.251 1720.96 L890.251 1720.96 L889.969 1720.96 L889.969 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="889.969,1720.96 889.969,1720.96 890.251,1720.96 889.969,1720.96 "/>
<path clip-path="url(#clip322)" d="M890.251 1720.76 L890.251 1720.96 L890.532 1720.96 L890.532 1720.76 L890.251 1720.76 L890.251 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="890.251,1720.76 890.251,1720.96 890.532,1720.96 890.532,1720.76 890.251,1720.76 "/>
<path clip-path="url(#clip322)" d="M890.532 1720.96 L890.532 1720.96 L890.814 1720.96 L890.814 1720.96 L890.532 1720.96 L890.532 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="890.532,1720.96 890.532,1720.96 890.814,1720.96 890.532,1720.96 "/>
<path clip-path="url(#clip322)" d="M890.814 1720.76 L890.814 1720.96 L891.096 1720.96 L891.096 1720.76 L890.814 1720.76 L890.814 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="890.814,1720.76 890.814,1720.96 891.096,1720.96 891.096,1720.76 890.814,1720.76 "/>
<path clip-path="url(#clip322)" d="M891.096 1719.97 L891.096 1720.96 L891.378 1720.96 L891.378 1719.97 L891.096 1719.97 L891.096 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="891.096,1719.97 891.096,1720.96 891.378,1720.96 891.378,1719.97 891.096,1719.97 "/>
<path clip-path="url(#clip322)" d="M891.378 1720.96 L891.378 1720.96 L891.659 1720.96 L891.659 1720.96 L891.378 1720.96 L891.378 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="891.378,1720.96 891.378,1720.96 891.659,1720.96 891.378,1720.96 "/>
<path clip-path="url(#clip322)" d="M891.659 1720.56 L891.659 1720.96 L891.941 1720.96 L891.941 1720.56 L891.659 1720.56 L891.659 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="891.659,1720.56 891.659,1720.96 891.941,1720.96 891.941,1720.56 891.659,1720.56 "/>
<path clip-path="url(#clip322)" d="M891.941 1720.56 L891.941 1720.96 L892.223 1720.96 L892.223 1720.56 L891.941 1720.56 L891.941 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="891.941,1720.56 891.941,1720.96 892.223,1720.96 892.223,1720.56 891.941,1720.56 "/>
<path clip-path="url(#clip322)" d="M892.223 1720.96 L892.223 1720.96 L892.505 1720.96 L892.505 1720.96 L892.223 1720.96 L892.223 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="892.223,1720.96 892.223,1720.96 892.505,1720.96 892.223,1720.96 "/>
<path clip-path="url(#clip322)" d="M892.505 1720.56 L892.505 1720.96 L892.786 1720.96 L892.786 1720.56 L892.505 1720.56 L892.505 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="892.505,1720.56 892.505,1720.96 892.786,1720.96 892.786,1720.56 892.505,1720.56 "/>
<path clip-path="url(#clip322)" d="M892.786 1719.58 L892.786 1720.96 L893.068 1720.96 L893.068 1719.58 L892.786 1719.58 L892.786 1719.58  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="892.786,1719.58 892.786,1720.96 893.068,1720.96 893.068,1719.58 892.786,1719.58 "/>
<path clip-path="url(#clip322)" d="M893.068 1720.56 L893.068 1720.96 L893.35 1720.96 L893.35 1720.56 L893.068 1720.56 L893.068 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="893.068,1720.56 893.068,1720.96 893.35,1720.96 893.35,1720.56 893.068,1720.56 "/>
<path clip-path="url(#clip322)" d="M893.35 1720.56 L893.35 1720.96 L893.631 1720.96 L893.631 1720.56 L893.35 1720.56 L893.35 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="893.35,1720.56 893.35,1720.96 893.631,1720.96 893.631,1720.56 893.35,1720.56 "/>
<path clip-path="url(#clip322)" d="M893.631 1720.76 L893.631 1720.96 L893.913 1720.96 L893.913 1720.76 L893.631 1720.76 L893.631 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="893.631,1720.76 893.631,1720.96 893.913,1720.96 893.913,1720.76 893.631,1720.76 "/>
<path clip-path="url(#clip322)" d="M893.913 1720.76 L893.913 1720.96 L894.195 1720.96 L894.195 1720.76 L893.913 1720.76 L893.913 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="893.913,1720.76 893.913,1720.96 894.195,1720.96 894.195,1720.76 893.913,1720.76 "/>
<path clip-path="url(#clip322)" d="M894.195 1720.96 L894.195 1720.96 L894.477 1720.96 L894.477 1720.96 L894.195 1720.96 L894.195 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="894.195,1720.96 894.195,1720.96 894.477,1720.96 894.195,1720.96 "/>
<path clip-path="url(#clip322)" d="M894.477 1720.76 L894.477 1720.96 L894.758 1720.96 L894.758 1720.76 L894.477 1720.76 L894.477 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="894.477,1720.76 894.477,1720.96 894.758,1720.96 894.758,1720.76 894.477,1720.76 "/>
<path clip-path="url(#clip322)" d="M894.758 1720.37 L894.758 1720.96 L895.04 1720.96 L895.04 1720.37 L894.758 1720.37 L894.758 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="894.758,1720.37 894.758,1720.96 895.04,1720.96 895.04,1720.37 894.758,1720.37 "/>
<path clip-path="url(#clip322)" d="M895.04 1720.76 L895.04 1720.96 L895.322 1720.96 L895.322 1720.76 L895.04 1720.76 L895.04 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="895.04,1720.76 895.04,1720.96 895.322,1720.96 895.322,1720.76 895.04,1720.76 "/>
<path clip-path="url(#clip322)" d="M895.322 1720.56 L895.322 1720.96 L895.604 1720.96 L895.604 1720.56 L895.322 1720.56 L895.322 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="895.322,1720.56 895.322,1720.96 895.604,1720.96 895.604,1720.56 895.322,1720.56 "/>
<path clip-path="url(#clip322)" d="M895.604 1720.76 L895.604 1720.96 L895.885 1720.96 L895.885 1720.76 L895.604 1720.76 L895.604 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="895.604,1720.76 895.604,1720.96 895.885,1720.96 895.885,1720.76 895.604,1720.76 "/>
<path clip-path="url(#clip322)" d="M895.885 1720.76 L895.885 1720.96 L896.167 1720.96 L896.167 1720.76 L895.885 1720.76 L895.885 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="895.885,1720.76 895.885,1720.96 896.167,1720.96 896.167,1720.76 895.885,1720.76 "/>
<path clip-path="url(#clip322)" d="M896.167 1719.58 L896.167 1720.96 L896.449 1720.96 L896.449 1719.58 L896.167 1719.58 L896.167 1719.58  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="896.167,1719.58 896.167,1720.96 896.449,1720.96 896.449,1719.58 896.167,1719.58 "/>
<path clip-path="url(#clip322)" d="M896.449 1720.17 L896.449 1720.96 L896.73 1720.96 L896.73 1720.17 L896.449 1720.17 L896.449 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="896.449,1720.17 896.449,1720.96 896.73,1720.96 896.73,1720.17 896.449,1720.17 "/>
<path clip-path="url(#clip322)" d="M896.73 1720.76 L896.73 1720.96 L897.012 1720.96 L897.012 1720.76 L896.73 1720.76 L896.73 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="896.73,1720.76 896.73,1720.96 897.012,1720.96 897.012,1720.76 896.73,1720.76 "/>
<path clip-path="url(#clip322)" d="M897.012 1720.56 L897.012 1720.96 L897.294 1720.96 L897.294 1720.56 L897.012 1720.56 L897.012 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="897.012,1720.56 897.012,1720.96 897.294,1720.96 897.294,1720.56 897.012,1720.56 "/>
<path clip-path="url(#clip322)" d="M897.294 1720.37 L897.294 1720.96 L897.576 1720.96 L897.576 1720.37 L897.294 1720.37 L897.294 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="897.294,1720.37 897.294,1720.96 897.576,1720.96 897.576,1720.37 897.294,1720.37 "/>
<path clip-path="url(#clip322)" d="M897.576 1720.56 L897.576 1720.96 L897.857 1720.96 L897.857 1720.56 L897.576 1720.56 L897.576 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="897.576,1720.56 897.576,1720.96 897.857,1720.96 897.857,1720.56 897.576,1720.56 "/>
<path clip-path="url(#clip322)" d="M897.857 1720.76 L897.857 1720.96 L898.139 1720.96 L898.139 1720.76 L897.857 1720.76 L897.857 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="897.857,1720.76 897.857,1720.96 898.139,1720.96 898.139,1720.76 897.857,1720.76 "/>
<path clip-path="url(#clip322)" d="M898.139 1720.56 L898.139 1720.96 L898.421 1720.96 L898.421 1720.56 L898.139 1720.56 L898.139 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="898.139,1720.56 898.139,1720.96 898.421,1720.96 898.421,1720.56 898.139,1720.56 "/>
<path clip-path="url(#clip322)" d="M898.421 1720.56 L898.421 1720.96 L898.702 1720.96 L898.702 1720.56 L898.421 1720.56 L898.421 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="898.421,1720.56 898.421,1720.96 898.702,1720.96 898.702,1720.56 898.421,1720.56 "/>
<path clip-path="url(#clip322)" d="M898.702 1720.76 L898.702 1720.96 L898.984 1720.96 L898.984 1720.76 L898.702 1720.76 L898.702 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="898.702,1720.76 898.702,1720.96 898.984,1720.96 898.984,1720.76 898.702,1720.76 "/>
<path clip-path="url(#clip322)" d="M898.984 1720.76 L898.984 1720.96 L899.266 1720.96 L899.266 1720.76 L898.984 1720.76 L898.984 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="898.984,1720.76 898.984,1720.96 899.266,1720.96 899.266,1720.76 898.984,1720.76 "/>
<path clip-path="url(#clip322)" d="M899.266 1720.56 L899.266 1720.96 L899.548 1720.96 L899.548 1720.56 L899.266 1720.56 L899.266 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="899.266,1720.56 899.266,1720.96 899.548,1720.96 899.548,1720.56 899.266,1720.56 "/>
<path clip-path="url(#clip322)" d="M899.548 1720.96 L899.548 1720.96 L899.829 1720.96 L899.829 1720.96 L899.548 1720.96 L899.548 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="899.548,1720.96 899.548,1720.96 899.829,1720.96 899.548,1720.96 "/>
<path clip-path="url(#clip322)" d="M899.829 1720.56 L899.829 1720.96 L900.111 1720.96 L900.111 1720.56 L899.829 1720.56 L899.829 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="899.829,1720.56 899.829,1720.96 900.111,1720.96 900.111,1720.56 899.829,1720.56 "/>
<path clip-path="url(#clip322)" d="M900.111 1720.56 L900.111 1720.96 L900.393 1720.96 L900.393 1720.56 L900.111 1720.56 L900.111 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="900.111,1720.56 900.111,1720.96 900.393,1720.96 900.393,1720.56 900.111,1720.56 "/>
<path clip-path="url(#clip322)" d="M900.393 1720.96 L900.393 1720.96 L900.675 1720.96 L900.675 1720.96 L900.393 1720.96 L900.393 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="900.393,1720.96 900.393,1720.96 900.675,1720.96 900.393,1720.96 "/>
<path clip-path="url(#clip322)" d="M900.675 1720.96 L900.675 1720.96 L900.956 1720.96 L900.956 1720.96 L900.675 1720.96 L900.675 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="900.675,1720.96 900.675,1720.96 900.956,1720.96 900.675,1720.96 "/>
<path clip-path="url(#clip322)" d="M900.956 1720.76 L900.956 1720.96 L901.238 1720.96 L901.238 1720.76 L900.956 1720.76 L900.956 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="900.956,1720.76 900.956,1720.96 901.238,1720.96 901.238,1720.76 900.956,1720.76 "/>
<path clip-path="url(#clip322)" d="M901.238 1720.56 L901.238 1720.96 L901.52 1720.96 L901.52 1720.56 L901.238 1720.56 L901.238 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="901.238,1720.56 901.238,1720.96 901.52,1720.96 901.52,1720.56 901.238,1720.56 "/>
<path clip-path="url(#clip322)" d="M901.52 1720.56 L901.52 1720.96 L901.801 1720.96 L901.801 1720.56 L901.52 1720.56 L901.52 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="901.52,1720.56 901.52,1720.96 901.801,1720.96 901.801,1720.56 901.52,1720.56 "/>
<path clip-path="url(#clip322)" d="M901.801 1720.96 L901.801 1720.96 L902.083 1720.96 L902.083 1720.96 L901.801 1720.96 L901.801 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="901.801,1720.96 901.801,1720.96 902.083,1720.96 901.801,1720.96 "/>
<path clip-path="url(#clip322)" d="M902.083 1720.56 L902.083 1720.96 L902.365 1720.96 L902.365 1720.56 L902.083 1720.56 L902.083 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="902.083,1720.56 902.083,1720.96 902.365,1720.96 902.365,1720.56 902.083,1720.56 "/>
<path clip-path="url(#clip322)" d="M902.365 1720.96 L902.365 1720.96 L902.647 1720.96 L902.647 1720.96 L902.365 1720.96 L902.365 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="902.365,1720.96 902.365,1720.96 902.647,1720.96 902.365,1720.96 "/>
<path clip-path="url(#clip322)" d="M902.647 1720.76 L902.647 1720.96 L902.928 1720.96 L902.928 1720.76 L902.647 1720.76 L902.647 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="902.647,1720.76 902.647,1720.96 902.928,1720.96 902.928,1720.76 902.647,1720.76 "/>
<path clip-path="url(#clip322)" d="M902.928 1720.17 L902.928 1720.96 L903.21 1720.96 L903.21 1720.17 L902.928 1720.17 L902.928 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="902.928,1720.17 902.928,1720.96 903.21,1720.96 903.21,1720.17 902.928,1720.17 "/>
<path clip-path="url(#clip322)" d="M903.21 1720.96 L903.21 1720.96 L903.492 1720.96 L903.492 1720.96 L903.21 1720.96 L903.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="903.21,1720.96 903.21,1720.96 903.492,1720.96 903.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M903.492 1720.96 L903.492 1720.96 L903.774 1720.96 L903.774 1720.96 L903.492 1720.96 L903.492 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="903.492,1720.96 903.492,1720.96 903.774,1720.96 903.492,1720.96 "/>
<path clip-path="url(#clip322)" d="M903.774 1720.76 L903.774 1720.96 L904.055 1720.96 L904.055 1720.76 L903.774 1720.76 L903.774 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="903.774,1720.76 903.774,1720.96 904.055,1720.96 904.055,1720.76 903.774,1720.76 "/>
<path clip-path="url(#clip322)" d="M904.055 1720.56 L904.055 1720.96 L904.337 1720.96 L904.337 1720.56 L904.055 1720.56 L904.055 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="904.055,1720.56 904.055,1720.96 904.337,1720.96 904.337,1720.56 904.055,1720.56 "/>
<path clip-path="url(#clip322)" d="M904.337 1720.37 L904.337 1720.96 L904.619 1720.96 L904.619 1720.37 L904.337 1720.37 L904.337 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="904.337,1720.37 904.337,1720.96 904.619,1720.96 904.619,1720.37 904.337,1720.37 "/>
<path clip-path="url(#clip322)" d="M904.619 1720.76 L904.619 1720.96 L904.9 1720.96 L904.9 1720.76 L904.619 1720.76 L904.619 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="904.619,1720.76 904.619,1720.96 904.9,1720.96 904.9,1720.76 904.619,1720.76 "/>
<path clip-path="url(#clip322)" d="M904.9 1720.76 L904.9 1720.96 L905.182 1720.96 L905.182 1720.76 L904.9 1720.76 L904.9 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="904.9,1720.76 904.9,1720.96 905.182,1720.96 905.182,1720.76 904.9,1720.76 "/>
<path clip-path="url(#clip322)" d="M905.182 1720.96 L905.182 1720.96 L905.464 1720.96 L905.464 1720.96 L905.182 1720.96 L905.182 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="905.182,1720.96 905.182,1720.96 905.464,1720.96 905.182,1720.96 "/>
<path clip-path="url(#clip322)" d="M905.464 1720.37 L905.464 1720.96 L905.746 1720.96 L905.746 1720.37 L905.464 1720.37 L905.464 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="905.464,1720.37 905.464,1720.96 905.746,1720.96 905.746,1720.37 905.464,1720.37 "/>
<path clip-path="url(#clip322)" d="M905.746 1720.76 L905.746 1720.96 L906.027 1720.96 L906.027 1720.76 L905.746 1720.76 L905.746 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="905.746,1720.76 905.746,1720.96 906.027,1720.96 906.027,1720.76 905.746,1720.76 "/>
<path clip-path="url(#clip322)" d="M906.027 1720.96 L906.027 1720.96 L906.309 1720.96 L906.309 1720.96 L906.027 1720.96 L906.027 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="906.027,1720.96 906.027,1720.96 906.309,1720.96 906.027,1720.96 "/>
<path clip-path="url(#clip322)" d="M906.309 1720.96 L906.309 1720.96 L906.591 1720.96 L906.591 1720.96 L906.309 1720.96 L906.309 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="906.309,1720.96 906.309,1720.96 906.591,1720.96 906.309,1720.96 "/>
<path clip-path="url(#clip322)" d="M906.591 1720.96 L906.591 1720.96 L906.873 1720.96 L906.873 1720.96 L906.591 1720.96 L906.591 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="906.591,1720.96 906.591,1720.96 906.873,1720.96 906.591,1720.96 "/>
<path clip-path="url(#clip322)" d="M906.873 1720.56 L906.873 1720.96 L907.154 1720.96 L907.154 1720.56 L906.873 1720.56 L906.873 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="906.873,1720.56 906.873,1720.96 907.154,1720.96 907.154,1720.56 906.873,1720.56 "/>
<path clip-path="url(#clip322)" d="M907.154 1720.76 L907.154 1720.96 L907.436 1720.96 L907.436 1720.76 L907.154 1720.76 L907.154 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="907.154,1720.76 907.154,1720.96 907.436,1720.96 907.436,1720.76 907.154,1720.76 "/>
<path clip-path="url(#clip322)" d="M907.436 1720.76 L907.436 1720.96 L907.718 1720.96 L907.718 1720.76 L907.436 1720.76 L907.436 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="907.436,1720.76 907.436,1720.96 907.718,1720.96 907.718,1720.76 907.436,1720.76 "/>
<path clip-path="url(#clip322)" d="M907.718 1720.76 L907.718 1720.96 L907.999 1720.96 L907.999 1720.76 L907.718 1720.76 L907.718 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="907.718,1720.76 907.718,1720.96 907.999,1720.96 907.999,1720.76 907.718,1720.76 "/>
<path clip-path="url(#clip322)" d="M907.999 1720.96 L907.999 1720.96 L908.281 1720.96 L908.281 1720.96 L907.999 1720.96 L907.999 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="907.999,1720.96 907.999,1720.96 908.281,1720.96 907.999,1720.96 "/>
<path clip-path="url(#clip322)" d="M908.281 1720.96 L908.281 1720.96 L908.563 1720.96 L908.563 1720.96 L908.281 1720.96 L908.281 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="908.281,1720.96 908.281,1720.96 908.563,1720.96 908.281,1720.96 "/>
<path clip-path="url(#clip322)" d="M908.563 1720.96 L908.563 1720.96 L908.845 1720.96 L908.845 1720.96 L908.563 1720.96 L908.563 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="908.563,1720.96 908.563,1720.96 908.845,1720.96 908.563,1720.96 "/>
<path clip-path="url(#clip322)" d="M908.845 1720.76 L908.845 1720.96 L909.126 1720.96 L909.126 1720.76 L908.845 1720.76 L908.845 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="908.845,1720.76 908.845,1720.96 909.126,1720.96 909.126,1720.76 908.845,1720.76 "/>
<path clip-path="url(#clip322)" d="M909.126 1720.96 L909.126 1720.96 L909.408 1720.96 L909.408 1720.96 L909.126 1720.96 L909.126 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="909.126,1720.96 909.126,1720.96 909.408,1720.96 909.126,1720.96 "/>
<path clip-path="url(#clip322)" d="M909.408 1720.76 L909.408 1720.96 L909.69 1720.96 L909.69 1720.76 L909.408 1720.76 L909.408 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="909.408,1720.76 909.408,1720.96 909.69,1720.96 909.69,1720.76 909.408,1720.76 "/>
<path clip-path="url(#clip322)" d="M909.69 1720.96 L909.69 1720.96 L909.972 1720.96 L909.972 1720.96 L909.69 1720.96 L909.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="909.69,1720.96 909.69,1720.96 909.972,1720.96 909.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M909.972 1720.76 L909.972 1720.96 L910.253 1720.96 L910.253 1720.76 L909.972 1720.76 L909.972 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="909.972,1720.76 909.972,1720.96 910.253,1720.96 910.253,1720.76 909.972,1720.76 "/>
<path clip-path="url(#clip322)" d="M910.253 1720.37 L910.253 1720.96 L910.535 1720.96 L910.535 1720.37 L910.253 1720.37 L910.253 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="910.253,1720.37 910.253,1720.96 910.535,1720.96 910.535,1720.37 910.253,1720.37 "/>
<path clip-path="url(#clip322)" d="M910.535 1720.96 L910.535 1720.96 L910.817 1720.96 L910.817 1720.96 L910.535 1720.96 L910.535 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="910.535,1720.96 910.535,1720.96 910.817,1720.96 910.535,1720.96 "/>
<path clip-path="url(#clip322)" d="M910.817 1720.56 L910.817 1720.96 L911.098 1720.96 L911.098 1720.56 L910.817 1720.56 L910.817 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="910.817,1720.56 910.817,1720.96 911.098,1720.96 911.098,1720.56 910.817,1720.56 "/>
<path clip-path="url(#clip322)" d="M911.098 1720.76 L911.098 1720.96 L911.38 1720.96 L911.38 1720.76 L911.098 1720.76 L911.098 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="911.098,1720.76 911.098,1720.96 911.38,1720.96 911.38,1720.76 911.098,1720.76 "/>
<path clip-path="url(#clip322)" d="M911.38 1720.56 L911.38 1720.96 L911.662 1720.96 L911.662 1720.56 L911.38 1720.56 L911.38 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="911.38,1720.56 911.38,1720.96 911.662,1720.96 911.662,1720.56 911.38,1720.56 "/>
<path clip-path="url(#clip322)" d="M911.662 1720.56 L911.662 1720.96 L911.944 1720.96 L911.944 1720.56 L911.662 1720.56 L911.662 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="911.662,1720.56 911.662,1720.96 911.944,1720.96 911.944,1720.56 911.662,1720.56 "/>
<path clip-path="url(#clip322)" d="M911.944 1720.76 L911.944 1720.96 L912.225 1720.96 L912.225 1720.76 L911.944 1720.76 L911.944 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="911.944,1720.76 911.944,1720.96 912.225,1720.96 912.225,1720.76 911.944,1720.76 "/>
<path clip-path="url(#clip322)" d="M912.225 1720.76 L912.225 1720.96 L912.507 1720.96 L912.507 1720.76 L912.225 1720.76 L912.225 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="912.225,1720.76 912.225,1720.96 912.507,1720.96 912.507,1720.76 912.225,1720.76 "/>
<path clip-path="url(#clip322)" d="M912.507 1720.76 L912.507 1720.96 L912.789 1720.96 L912.789 1720.76 L912.507 1720.76 L912.507 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="912.507,1720.76 912.507,1720.96 912.789,1720.96 912.789,1720.76 912.507,1720.76 "/>
<path clip-path="url(#clip322)" d="M912.789 1720.37 L912.789 1720.96 L913.07 1720.96 L913.07 1720.37 L912.789 1720.37 L912.789 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="912.789,1720.37 912.789,1720.96 913.07,1720.96 913.07,1720.37 912.789,1720.37 "/>
<path clip-path="url(#clip322)" d="M913.07 1720.96 L913.07 1720.96 L913.352 1720.96 L913.352 1720.96 L913.07 1720.96 L913.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="913.07,1720.96 913.07,1720.96 913.352,1720.96 913.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M913.352 1720.76 L913.352 1720.96 L913.634 1720.96 L913.634 1720.76 L913.352 1720.76 L913.352 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="913.352,1720.76 913.352,1720.96 913.634,1720.96 913.634,1720.76 913.352,1720.76 "/>
<path clip-path="url(#clip322)" d="M913.634 1720.17 L913.634 1720.96 L913.916 1720.96 L913.916 1720.17 L913.634 1720.17 L913.634 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="913.634,1720.17 913.634,1720.96 913.916,1720.96 913.916,1720.17 913.634,1720.17 "/>
<path clip-path="url(#clip322)" d="M913.916 1720.76 L913.916 1720.96 L914.197 1720.96 L914.197 1720.76 L913.916 1720.76 L913.916 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="913.916,1720.76 913.916,1720.96 914.197,1720.96 914.197,1720.76 913.916,1720.76 "/>
<path clip-path="url(#clip322)" d="M914.197 1720.37 L914.197 1720.96 L914.479 1720.96 L914.479 1720.37 L914.197 1720.37 L914.197 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="914.197,1720.37 914.197,1720.96 914.479,1720.96 914.479,1720.37 914.197,1720.37 "/>
<path clip-path="url(#clip322)" d="M914.479 1720.56 L914.479 1720.96 L914.761 1720.96 L914.761 1720.56 L914.479 1720.56 L914.479 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="914.479,1720.56 914.479,1720.96 914.761,1720.96 914.761,1720.56 914.479,1720.56 "/>
<path clip-path="url(#clip322)" d="M914.761 1720.76 L914.761 1720.96 L915.043 1720.96 L915.043 1720.76 L914.761 1720.76 L914.761 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="914.761,1720.76 914.761,1720.96 915.043,1720.96 915.043,1720.76 914.761,1720.76 "/>
<path clip-path="url(#clip322)" d="M915.043 1720.76 L915.043 1720.96 L915.324 1720.96 L915.324 1720.76 L915.043 1720.76 L915.043 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="915.043,1720.76 915.043,1720.96 915.324,1720.96 915.324,1720.76 915.043,1720.76 "/>
<path clip-path="url(#clip322)" d="M915.324 1720.96 L915.324 1720.96 L915.606 1720.96 L915.606 1720.96 L915.324 1720.96 L915.324 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="915.324,1720.96 915.324,1720.96 915.606,1720.96 915.324,1720.96 "/>
<path clip-path="url(#clip322)" d="M915.606 1720.76 L915.606 1720.96 L915.888 1720.96 L915.888 1720.76 L915.606 1720.76 L915.606 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="915.606,1720.76 915.606,1720.96 915.888,1720.96 915.888,1720.76 915.606,1720.76 "/>
<path clip-path="url(#clip322)" d="M915.888 1720.56 L915.888 1720.96 L916.169 1720.96 L916.169 1720.56 L915.888 1720.56 L915.888 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="915.888,1720.56 915.888,1720.96 916.169,1720.96 916.169,1720.56 915.888,1720.56 "/>
<path clip-path="url(#clip322)" d="M916.169 1720.76 L916.169 1720.96 L916.451 1720.96 L916.451 1720.76 L916.169 1720.76 L916.169 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="916.169,1720.76 916.169,1720.96 916.451,1720.96 916.451,1720.76 916.169,1720.76 "/>
<path clip-path="url(#clip322)" d="M916.451 1720.56 L916.451 1720.96 L916.733 1720.96 L916.733 1720.56 L916.451 1720.56 L916.451 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="916.451,1720.56 916.451,1720.96 916.733,1720.96 916.733,1720.56 916.451,1720.56 "/>
<path clip-path="url(#clip322)" d="M916.733 1720.76 L916.733 1720.96 L917.015 1720.96 L917.015 1720.76 L916.733 1720.76 L916.733 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="916.733,1720.76 916.733,1720.96 917.015,1720.96 917.015,1720.76 916.733,1720.76 "/>
<path clip-path="url(#clip322)" d="M917.015 1720.17 L917.015 1720.96 L917.296 1720.96 L917.296 1720.17 L917.015 1720.17 L917.015 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="917.015,1720.17 917.015,1720.96 917.296,1720.96 917.296,1720.17 917.015,1720.17 "/>
<path clip-path="url(#clip322)" d="M917.296 1720.76 L917.296 1720.96 L917.578 1720.96 L917.578 1720.76 L917.296 1720.76 L917.296 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="917.296,1720.76 917.296,1720.96 917.578,1720.96 917.578,1720.76 917.296,1720.76 "/>
<path clip-path="url(#clip322)" d="M917.578 1720.37 L917.578 1720.96 L917.86 1720.96 L917.86 1720.37 L917.578 1720.37 L917.578 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="917.578,1720.37 917.578,1720.96 917.86,1720.96 917.86,1720.37 917.578,1720.37 "/>
<path clip-path="url(#clip322)" d="M917.86 1720.37 L917.86 1720.96 L918.142 1720.96 L918.142 1720.37 L917.86 1720.37 L917.86 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="917.86,1720.37 917.86,1720.96 918.142,1720.96 918.142,1720.37 917.86,1720.37 "/>
<path clip-path="url(#clip322)" d="M918.142 1720.56 L918.142 1720.96 L918.423 1720.96 L918.423 1720.56 L918.142 1720.56 L918.142 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="918.142,1720.56 918.142,1720.96 918.423,1720.96 918.423,1720.56 918.142,1720.56 "/>
<path clip-path="url(#clip322)" d="M918.423 1720.56 L918.423 1720.96 L918.705 1720.96 L918.705 1720.56 L918.423 1720.56 L918.423 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="918.423,1720.56 918.423,1720.96 918.705,1720.96 918.705,1720.56 918.423,1720.56 "/>
<path clip-path="url(#clip322)" d="M918.705 1720.56 L918.705 1720.96 L918.987 1720.96 L918.987 1720.56 L918.705 1720.56 L918.705 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="918.705,1720.56 918.705,1720.96 918.987,1720.96 918.987,1720.56 918.705,1720.56 "/>
<path clip-path="url(#clip322)" d="M918.987 1720.56 L918.987 1720.96 L919.268 1720.96 L919.268 1720.56 L918.987 1720.56 L918.987 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="918.987,1720.56 918.987,1720.96 919.268,1720.96 919.268,1720.56 918.987,1720.56 "/>
<path clip-path="url(#clip322)" d="M919.268 1720.76 L919.268 1720.96 L919.55 1720.96 L919.55 1720.76 L919.268 1720.76 L919.268 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="919.268,1720.76 919.268,1720.96 919.55,1720.96 919.55,1720.76 919.268,1720.76 "/>
<path clip-path="url(#clip322)" d="M919.55 1720.96 L919.55 1720.96 L919.832 1720.96 L919.832 1720.96 L919.55 1720.96 L919.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="919.55,1720.96 919.55,1720.96 919.832,1720.96 919.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M919.832 1720.76 L919.832 1720.96 L920.114 1720.96 L920.114 1720.76 L919.832 1720.76 L919.832 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="919.832,1720.76 919.832,1720.96 920.114,1720.96 920.114,1720.76 919.832,1720.76 "/>
<path clip-path="url(#clip322)" d="M920.114 1720.56 L920.114 1720.96 L920.395 1720.96 L920.395 1720.56 L920.114 1720.56 L920.114 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="920.114,1720.56 920.114,1720.96 920.395,1720.96 920.395,1720.56 920.114,1720.56 "/>
<path clip-path="url(#clip322)" d="M920.395 1720.76 L920.395 1720.96 L920.677 1720.96 L920.677 1720.76 L920.395 1720.76 L920.395 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="920.395,1720.76 920.395,1720.96 920.677,1720.96 920.677,1720.76 920.395,1720.76 "/>
<path clip-path="url(#clip322)" d="M920.677 1720.56 L920.677 1720.96 L920.959 1720.96 L920.959 1720.56 L920.677 1720.56 L920.677 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="920.677,1720.56 920.677,1720.96 920.959,1720.96 920.959,1720.56 920.677,1720.56 "/>
<path clip-path="url(#clip322)" d="M920.959 1720.17 L920.959 1720.96 L921.241 1720.96 L921.241 1720.17 L920.959 1720.17 L920.959 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="920.959,1720.17 920.959,1720.96 921.241,1720.96 921.241,1720.17 920.959,1720.17 "/>
<path clip-path="url(#clip322)" d="M921.241 1720.76 L921.241 1720.96 L921.522 1720.96 L921.522 1720.76 L921.241 1720.76 L921.241 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="921.241,1720.76 921.241,1720.96 921.522,1720.96 921.522,1720.76 921.241,1720.76 "/>
<path clip-path="url(#clip322)" d="M921.522 1720.76 L921.522 1720.96 L921.804 1720.96 L921.804 1720.76 L921.522 1720.76 L921.522 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="921.522,1720.76 921.522,1720.96 921.804,1720.96 921.804,1720.76 921.522,1720.76 "/>
<path clip-path="url(#clip322)" d="M921.804 1720.37 L921.804 1720.96 L922.086 1720.96 L922.086 1720.37 L921.804 1720.37 L921.804 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="921.804,1720.37 921.804,1720.96 922.086,1720.96 922.086,1720.37 921.804,1720.37 "/>
<path clip-path="url(#clip322)" d="M922.086 1720.37 L922.086 1720.96 L922.367 1720.96 L922.367 1720.37 L922.086 1720.37 L922.086 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="922.086,1720.37 922.086,1720.96 922.367,1720.96 922.367,1720.37 922.086,1720.37 "/>
<path clip-path="url(#clip322)" d="M922.367 1720.56 L922.367 1720.96 L922.649 1720.96 L922.649 1720.56 L922.367 1720.56 L922.367 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="922.367,1720.56 922.367,1720.96 922.649,1720.96 922.649,1720.56 922.367,1720.56 "/>
<path clip-path="url(#clip322)" d="M922.649 1720.76 L922.649 1720.96 L922.931 1720.96 L922.931 1720.76 L922.649 1720.76 L922.649 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="922.649,1720.76 922.649,1720.96 922.931,1720.96 922.931,1720.76 922.649,1720.76 "/>
<path clip-path="url(#clip322)" d="M922.931 1720.76 L922.931 1720.96 L923.213 1720.96 L923.213 1720.76 L922.931 1720.76 L922.931 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="922.931,1720.76 922.931,1720.96 923.213,1720.96 923.213,1720.76 922.931,1720.76 "/>
<path clip-path="url(#clip322)" d="M923.213 1720.56 L923.213 1720.96 L923.494 1720.96 L923.494 1720.56 L923.213 1720.56 L923.213 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="923.213,1720.56 923.213,1720.96 923.494,1720.96 923.494,1720.56 923.213,1720.56 "/>
<path clip-path="url(#clip322)" d="M923.494 1720.76 L923.494 1720.96 L923.776 1720.96 L923.776 1720.76 L923.494 1720.76 L923.494 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="923.494,1720.76 923.494,1720.96 923.776,1720.96 923.776,1720.76 923.494,1720.76 "/>
<path clip-path="url(#clip322)" d="M923.776 1720.96 L923.776 1720.96 L924.058 1720.96 L924.058 1720.96 L923.776 1720.96 L923.776 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="923.776,1720.96 923.776,1720.96 924.058,1720.96 923.776,1720.96 "/>
<path clip-path="url(#clip322)" d="M924.058 1720.37 L924.058 1720.96 L924.34 1720.96 L924.34 1720.37 L924.058 1720.37 L924.058 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="924.058,1720.37 924.058,1720.96 924.34,1720.96 924.34,1720.37 924.058,1720.37 "/>
<path clip-path="url(#clip322)" d="M924.34 1720.56 L924.34 1720.96 L924.621 1720.96 L924.621 1720.56 L924.34 1720.56 L924.34 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="924.34,1720.56 924.34,1720.96 924.621,1720.96 924.621,1720.56 924.34,1720.56 "/>
<path clip-path="url(#clip322)" d="M924.621 1720.76 L924.621 1720.96 L924.903 1720.96 L924.903 1720.76 L924.621 1720.76 L924.621 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="924.621,1720.76 924.621,1720.96 924.903,1720.96 924.903,1720.76 924.621,1720.76 "/>
<path clip-path="url(#clip322)" d="M924.903 1720.37 L924.903 1720.96 L925.185 1720.96 L925.185 1720.37 L924.903 1720.37 L924.903 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="924.903,1720.37 924.903,1720.96 925.185,1720.96 925.185,1720.37 924.903,1720.37 "/>
<path clip-path="url(#clip322)" d="M925.185 1720.37 L925.185 1720.96 L925.466 1720.96 L925.466 1720.37 L925.185 1720.37 L925.185 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="925.185,1720.37 925.185,1720.96 925.466,1720.96 925.466,1720.37 925.185,1720.37 "/>
<path clip-path="url(#clip322)" d="M925.466 1720.56 L925.466 1720.96 L925.748 1720.96 L925.748 1720.56 L925.466 1720.56 L925.466 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="925.466,1720.56 925.466,1720.96 925.748,1720.96 925.748,1720.56 925.466,1720.56 "/>
<path clip-path="url(#clip322)" d="M925.748 1720.96 L925.748 1720.96 L926.03 1720.96 L926.03 1720.96 L925.748 1720.96 L925.748 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="925.748,1720.96 925.748,1720.96 926.03,1720.96 925.748,1720.96 "/>
<path clip-path="url(#clip322)" d="M926.03 1719.97 L926.03 1720.96 L926.312 1720.96 L926.312 1719.97 L926.03 1719.97 L926.03 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="926.03,1719.97 926.03,1720.96 926.312,1720.96 926.312,1719.97 926.03,1719.97 "/>
<path clip-path="url(#clip322)" d="M926.312 1720.56 L926.312 1720.96 L926.593 1720.96 L926.593 1720.56 L926.312 1720.56 L926.312 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="926.312,1720.56 926.312,1720.96 926.593,1720.96 926.593,1720.56 926.312,1720.56 "/>
<path clip-path="url(#clip322)" d="M926.593 1720.56 L926.593 1720.96 L926.875 1720.96 L926.875 1720.56 L926.593 1720.56 L926.593 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="926.593,1720.56 926.593,1720.96 926.875,1720.96 926.875,1720.56 926.593,1720.56 "/>
<path clip-path="url(#clip322)" d="M926.875 1720.56 L926.875 1720.96 L927.157 1720.96 L927.157 1720.56 L926.875 1720.56 L926.875 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="926.875,1720.56 926.875,1720.96 927.157,1720.96 927.157,1720.56 926.875,1720.56 "/>
<path clip-path="url(#clip322)" d="M927.157 1720.56 L927.157 1720.96 L927.439 1720.96 L927.439 1720.56 L927.157 1720.56 L927.157 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="927.157,1720.56 927.157,1720.96 927.439,1720.96 927.439,1720.56 927.157,1720.56 "/>
<path clip-path="url(#clip322)" d="M927.439 1720.56 L927.439 1720.96 L927.72 1720.96 L927.72 1720.56 L927.439 1720.56 L927.439 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="927.439,1720.56 927.439,1720.96 927.72,1720.96 927.72,1720.56 927.439,1720.56 "/>
<path clip-path="url(#clip322)" d="M927.72 1720.96 L927.72 1720.96 L928.002 1720.96 L928.002 1720.96 L927.72 1720.96 L927.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="927.72,1720.96 927.72,1720.96 928.002,1720.96 927.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M928.002 1720.56 L928.002 1720.96 L928.284 1720.96 L928.284 1720.56 L928.002 1720.56 L928.002 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="928.002,1720.56 928.002,1720.96 928.284,1720.96 928.284,1720.56 928.002,1720.56 "/>
<path clip-path="url(#clip322)" d="M928.284 1720.96 L928.284 1720.96 L928.565 1720.96 L928.565 1720.96 L928.284 1720.96 L928.284 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="928.284,1720.96 928.284,1720.96 928.565,1720.96 928.284,1720.96 "/>
<path clip-path="url(#clip322)" d="M928.565 1720.76 L928.565 1720.96 L928.847 1720.96 L928.847 1720.76 L928.565 1720.76 L928.565 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="928.565,1720.76 928.565,1720.96 928.847,1720.96 928.847,1720.76 928.565,1720.76 "/>
<path clip-path="url(#clip322)" d="M928.847 1720.56 L928.847 1720.96 L929.129 1720.96 L929.129 1720.56 L928.847 1720.56 L928.847 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="928.847,1720.56 928.847,1720.96 929.129,1720.96 929.129,1720.56 928.847,1720.56 "/>
<path clip-path="url(#clip322)" d="M929.129 1720.56 L929.129 1720.96 L929.411 1720.96 L929.411 1720.56 L929.129 1720.56 L929.129 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="929.129,1720.56 929.129,1720.96 929.411,1720.96 929.411,1720.56 929.129,1720.56 "/>
<path clip-path="url(#clip322)" d="M929.411 1720.96 L929.411 1720.96 L929.692 1720.96 L929.692 1720.96 L929.411 1720.96 L929.411 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="929.411,1720.96 929.411,1720.96 929.692,1720.96 929.411,1720.96 "/>
<path clip-path="url(#clip322)" d="M929.692 1720.17 L929.692 1720.96 L929.974 1720.96 L929.974 1720.17 L929.692 1720.17 L929.692 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="929.692,1720.17 929.692,1720.96 929.974,1720.96 929.974,1720.17 929.692,1720.17 "/>
<path clip-path="url(#clip322)" d="M929.974 1720.37 L929.974 1720.96 L930.256 1720.96 L930.256 1720.37 L929.974 1720.37 L929.974 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="929.974,1720.37 929.974,1720.96 930.256,1720.96 930.256,1720.37 929.974,1720.37 "/>
<path clip-path="url(#clip322)" d="M930.256 1720.56 L930.256 1720.96 L930.537 1720.96 L930.537 1720.56 L930.256 1720.56 L930.256 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="930.256,1720.56 930.256,1720.96 930.537,1720.96 930.537,1720.56 930.256,1720.56 "/>
<path clip-path="url(#clip322)" d="M930.537 1720.76 L930.537 1720.96 L930.819 1720.96 L930.819 1720.76 L930.537 1720.76 L930.537 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="930.537,1720.76 930.537,1720.96 930.819,1720.96 930.819,1720.76 930.537,1720.76 "/>
<path clip-path="url(#clip322)" d="M930.819 1720.56 L930.819 1720.96 L931.101 1720.96 L931.101 1720.56 L930.819 1720.56 L930.819 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="930.819,1720.56 930.819,1720.96 931.101,1720.96 931.101,1720.56 930.819,1720.56 "/>
<path clip-path="url(#clip322)" d="M931.101 1720.56 L931.101 1720.96 L931.383 1720.96 L931.383 1720.56 L931.101 1720.56 L931.101 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="931.101,1720.56 931.101,1720.96 931.383,1720.96 931.383,1720.56 931.101,1720.56 "/>
<path clip-path="url(#clip322)" d="M931.383 1720.56 L931.383 1720.96 L931.664 1720.96 L931.664 1720.56 L931.383 1720.56 L931.383 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="931.383,1720.56 931.383,1720.96 931.664,1720.96 931.664,1720.56 931.383,1720.56 "/>
<path clip-path="url(#clip322)" d="M931.664 1720.56 L931.664 1720.96 L931.946 1720.96 L931.946 1720.56 L931.664 1720.56 L931.664 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="931.664,1720.56 931.664,1720.96 931.946,1720.96 931.946,1720.56 931.664,1720.56 "/>
<path clip-path="url(#clip322)" d="M931.946 1720.56 L931.946 1720.96 L932.228 1720.96 L932.228 1720.56 L931.946 1720.56 L931.946 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="931.946,1720.56 931.946,1720.96 932.228,1720.96 932.228,1720.56 931.946,1720.56 "/>
<path clip-path="url(#clip322)" d="M932.228 1720.56 L932.228 1720.96 L932.51 1720.96 L932.51 1720.56 L932.228 1720.56 L932.228 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="932.228,1720.56 932.228,1720.96 932.51,1720.96 932.51,1720.56 932.228,1720.56 "/>
<path clip-path="url(#clip322)" d="M932.51 1720.37 L932.51 1720.96 L932.791 1720.96 L932.791 1720.37 L932.51 1720.37 L932.51 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="932.51,1720.37 932.51,1720.96 932.791,1720.96 932.791,1720.37 932.51,1720.37 "/>
<path clip-path="url(#clip322)" d="M932.791 1720.56 L932.791 1720.96 L933.073 1720.96 L933.073 1720.56 L932.791 1720.56 L932.791 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="932.791,1720.56 932.791,1720.96 933.073,1720.96 933.073,1720.56 932.791,1720.56 "/>
<path clip-path="url(#clip322)" d="M933.073 1720.96 L933.073 1720.96 L933.355 1720.96 L933.355 1720.96 L933.073 1720.96 L933.073 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="933.073,1720.96 933.073,1720.96 933.355,1720.96 933.073,1720.96 "/>
<path clip-path="url(#clip322)" d="M933.355 1720.96 L933.355 1720.96 L933.636 1720.96 L933.636 1720.96 L933.355 1720.96 L933.355 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="933.355,1720.96 933.355,1720.96 933.636,1720.96 933.355,1720.96 "/>
<path clip-path="url(#clip322)" d="M933.636 1720.76 L933.636 1720.96 L933.918 1720.96 L933.918 1720.76 L933.636 1720.76 L933.636 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="933.636,1720.76 933.636,1720.96 933.918,1720.96 933.918,1720.76 933.636,1720.76 "/>
<path clip-path="url(#clip322)" d="M933.918 1720.96 L933.918 1720.96 L934.2 1720.96 L934.2 1720.96 L933.918 1720.96 L933.918 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="933.918,1720.96 933.918,1720.96 934.2,1720.96 933.918,1720.96 "/>
<path clip-path="url(#clip322)" d="M934.2 1720.56 L934.2 1720.96 L934.482 1720.96 L934.482 1720.56 L934.2 1720.56 L934.2 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="934.2,1720.56 934.2,1720.96 934.482,1720.96 934.482,1720.56 934.2,1720.56 "/>
<path clip-path="url(#clip322)" d="M934.482 1720.56 L934.482 1720.96 L934.763 1720.96 L934.763 1720.56 L934.482 1720.56 L934.482 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="934.482,1720.56 934.482,1720.96 934.763,1720.96 934.763,1720.56 934.482,1720.56 "/>
<path clip-path="url(#clip322)" d="M934.763 1720.76 L934.763 1720.96 L935.045 1720.96 L935.045 1720.76 L934.763 1720.76 L934.763 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="934.763,1720.76 934.763,1720.96 935.045,1720.96 935.045,1720.76 934.763,1720.76 "/>
<path clip-path="url(#clip322)" d="M935.045 1720.37 L935.045 1720.96 L935.327 1720.96 L935.327 1720.37 L935.045 1720.37 L935.045 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="935.045,1720.37 935.045,1720.96 935.327,1720.96 935.327,1720.37 935.045,1720.37 "/>
<path clip-path="url(#clip322)" d="M935.327 1720.76 L935.327 1720.96 L935.609 1720.96 L935.609 1720.76 L935.327 1720.76 L935.327 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="935.327,1720.76 935.327,1720.96 935.609,1720.96 935.609,1720.76 935.327,1720.76 "/>
<path clip-path="url(#clip322)" d="M935.609 1720.76 L935.609 1720.96 L935.89 1720.96 L935.89 1720.76 L935.609 1720.76 L935.609 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="935.609,1720.76 935.609,1720.96 935.89,1720.96 935.89,1720.76 935.609,1720.76 "/>
<path clip-path="url(#clip322)" d="M935.89 1720.56 L935.89 1720.96 L936.172 1720.96 L936.172 1720.56 L935.89 1720.56 L935.89 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="935.89,1720.56 935.89,1720.96 936.172,1720.96 936.172,1720.56 935.89,1720.56 "/>
<path clip-path="url(#clip322)" d="M936.172 1720.96 L936.172 1720.96 L936.454 1720.96 L936.454 1720.96 L936.172 1720.96 L936.172 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="936.172,1720.96 936.172,1720.96 936.454,1720.96 936.172,1720.96 "/>
<path clip-path="url(#clip322)" d="M936.454 1720.56 L936.454 1720.96 L936.735 1720.96 L936.735 1720.56 L936.454 1720.56 L936.454 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="936.454,1720.56 936.454,1720.96 936.735,1720.96 936.735,1720.56 936.454,1720.56 "/>
<path clip-path="url(#clip322)" d="M936.735 1720.76 L936.735 1720.96 L937.017 1720.96 L937.017 1720.76 L936.735 1720.76 L936.735 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="936.735,1720.76 936.735,1720.96 937.017,1720.96 937.017,1720.76 936.735,1720.76 "/>
<path clip-path="url(#clip322)" d="M937.017 1720.96 L937.017 1720.96 L937.299 1720.96 L937.299 1720.96 L937.017 1720.96 L937.017 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="937.017,1720.96 937.017,1720.96 937.299,1720.96 937.017,1720.96 "/>
<path clip-path="url(#clip322)" d="M937.299 1720.96 L937.299 1720.96 L937.581 1720.96 L937.581 1720.96 L937.299 1720.96 L937.299 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="937.299,1720.96 937.299,1720.96 937.581,1720.96 937.299,1720.96 "/>
<path clip-path="url(#clip322)" d="M937.581 1720.76 L937.581 1720.96 L937.862 1720.96 L937.862 1720.76 L937.581 1720.76 L937.581 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="937.581,1720.76 937.581,1720.96 937.862,1720.96 937.862,1720.76 937.581,1720.76 "/>
<path clip-path="url(#clip322)" d="M937.862 1720.76 L937.862 1720.96 L938.144 1720.96 L938.144 1720.76 L937.862 1720.76 L937.862 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="937.862,1720.76 937.862,1720.96 938.144,1720.96 938.144,1720.76 937.862,1720.76 "/>
<path clip-path="url(#clip322)" d="M938.144 1720.37 L938.144 1720.96 L938.426 1720.96 L938.426 1720.37 L938.144 1720.37 L938.144 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="938.144,1720.37 938.144,1720.96 938.426,1720.96 938.426,1720.37 938.144,1720.37 "/>
<path clip-path="url(#clip322)" d="M938.426 1720.96 L938.426 1720.96 L938.708 1720.96 L938.708 1720.96 L938.426 1720.96 L938.426 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="938.426,1720.96 938.426,1720.96 938.708,1720.96 938.426,1720.96 "/>
<path clip-path="url(#clip322)" d="M938.708 1720.76 L938.708 1720.96 L938.989 1720.96 L938.989 1720.76 L938.708 1720.76 L938.708 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="938.708,1720.76 938.708,1720.96 938.989,1720.96 938.989,1720.76 938.708,1720.76 "/>
<path clip-path="url(#clip322)" d="M938.989 1720.56 L938.989 1720.96 L939.271 1720.96 L939.271 1720.56 L938.989 1720.56 L938.989 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="938.989,1720.56 938.989,1720.96 939.271,1720.96 939.271,1720.56 938.989,1720.56 "/>
<path clip-path="url(#clip322)" d="M939.271 1720.76 L939.271 1720.96 L939.553 1720.96 L939.553 1720.76 L939.271 1720.76 L939.271 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="939.271,1720.76 939.271,1720.96 939.553,1720.96 939.553,1720.76 939.271,1720.76 "/>
<path clip-path="url(#clip322)" d="M939.553 1720.37 L939.553 1720.96 L939.834 1720.96 L939.834 1720.37 L939.553 1720.37 L939.553 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="939.553,1720.37 939.553,1720.96 939.834,1720.96 939.834,1720.37 939.553,1720.37 "/>
<path clip-path="url(#clip322)" d="M939.834 1720.76 L939.834 1720.96 L940.116 1720.96 L940.116 1720.76 L939.834 1720.76 L939.834 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="939.834,1720.76 939.834,1720.96 940.116,1720.96 940.116,1720.76 939.834,1720.76 "/>
<path clip-path="url(#clip322)" d="M940.116 1720.96 L940.116 1720.96 L940.398 1720.96 L940.398 1720.96 L940.116 1720.96 L940.116 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="940.116,1720.96 940.116,1720.96 940.398,1720.96 940.116,1720.96 "/>
<path clip-path="url(#clip322)" d="M940.398 1720.56 L940.398 1720.96 L940.68 1720.96 L940.68 1720.56 L940.398 1720.56 L940.398 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="940.398,1720.56 940.398,1720.96 940.68,1720.96 940.68,1720.56 940.398,1720.56 "/>
<path clip-path="url(#clip322)" d="M940.68 1720.76 L940.68 1720.96 L940.961 1720.96 L940.961 1720.76 L940.68 1720.76 L940.68 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="940.68,1720.76 940.68,1720.96 940.961,1720.96 940.961,1720.76 940.68,1720.76 "/>
<path clip-path="url(#clip322)" d="M940.961 1720.56 L940.961 1720.96 L941.243 1720.96 L941.243 1720.56 L940.961 1720.56 L940.961 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="940.961,1720.56 940.961,1720.96 941.243,1720.96 941.243,1720.56 940.961,1720.56 "/>
<path clip-path="url(#clip322)" d="M941.243 1720.56 L941.243 1720.96 L941.525 1720.96 L941.525 1720.56 L941.243 1720.56 L941.243 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="941.243,1720.56 941.243,1720.96 941.525,1720.96 941.525,1720.56 941.243,1720.56 "/>
<path clip-path="url(#clip322)" d="M941.525 1720.76 L941.525 1720.96 L941.807 1720.96 L941.807 1720.76 L941.525 1720.76 L941.525 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="941.525,1720.76 941.525,1720.96 941.807,1720.96 941.807,1720.76 941.525,1720.76 "/>
<path clip-path="url(#clip322)" d="M941.807 1720.56 L941.807 1720.96 L942.088 1720.96 L942.088 1720.56 L941.807 1720.56 L941.807 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="941.807,1720.56 941.807,1720.96 942.088,1720.96 942.088,1720.56 941.807,1720.56 "/>
<path clip-path="url(#clip322)" d="M942.088 1720.56 L942.088 1720.96 L942.37 1720.96 L942.37 1720.56 L942.088 1720.56 L942.088 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="942.088,1720.56 942.088,1720.96 942.37,1720.96 942.37,1720.56 942.088,1720.56 "/>
<path clip-path="url(#clip322)" d="M942.37 1720.76 L942.37 1720.96 L942.652 1720.96 L942.652 1720.76 L942.37 1720.76 L942.37 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="942.37,1720.76 942.37,1720.96 942.652,1720.96 942.652,1720.76 942.37,1720.76 "/>
<path clip-path="url(#clip322)" d="M942.652 1720.37 L942.652 1720.96 L942.933 1720.96 L942.933 1720.37 L942.652 1720.37 L942.652 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="942.652,1720.37 942.652,1720.96 942.933,1720.96 942.933,1720.37 942.652,1720.37 "/>
<path clip-path="url(#clip322)" d="M942.933 1720.96 L942.933 1720.96 L943.215 1720.96 L943.215 1720.96 L942.933 1720.96 L942.933 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="942.933,1720.96 942.933,1720.96 943.215,1720.96 942.933,1720.96 "/>
<path clip-path="url(#clip322)" d="M943.215 1720.76 L943.215 1720.96 L943.497 1720.96 L943.497 1720.76 L943.215 1720.76 L943.215 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="943.215,1720.76 943.215,1720.96 943.497,1720.96 943.497,1720.76 943.215,1720.76 "/>
<path clip-path="url(#clip322)" d="M943.497 1720.56 L943.497 1720.96 L943.779 1720.96 L943.779 1720.56 L943.497 1720.56 L943.497 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="943.497,1720.56 943.497,1720.96 943.779,1720.96 943.779,1720.56 943.497,1720.56 "/>
<path clip-path="url(#clip322)" d="M943.779 1720.96 L943.779 1720.96 L944.06 1720.96 L944.06 1720.96 L943.779 1720.96 L943.779 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="943.779,1720.96 943.779,1720.96 944.06,1720.96 943.779,1720.96 "/>
<path clip-path="url(#clip322)" d="M944.06 1720.37 L944.06 1720.96 L944.342 1720.96 L944.342 1720.37 L944.06 1720.37 L944.06 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="944.06,1720.37 944.06,1720.96 944.342,1720.96 944.342,1720.37 944.06,1720.37 "/>
<path clip-path="url(#clip322)" d="M944.342 1720.96 L944.342 1720.96 L944.624 1720.96 L944.624 1720.96 L944.342 1720.96 L944.342 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="944.342,1720.96 944.342,1720.96 944.624,1720.96 944.342,1720.96 "/>
<path clip-path="url(#clip322)" d="M944.624 1720.76 L944.624 1720.96 L944.905 1720.96 L944.905 1720.76 L944.624 1720.76 L944.624 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="944.624,1720.76 944.624,1720.96 944.905,1720.96 944.905,1720.76 944.624,1720.76 "/>
<path clip-path="url(#clip322)" d="M944.905 1720.76 L944.905 1720.96 L945.187 1720.96 L945.187 1720.76 L944.905 1720.76 L944.905 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="944.905,1720.76 944.905,1720.96 945.187,1720.96 945.187,1720.76 944.905,1720.76 "/>
<path clip-path="url(#clip322)" d="M945.187 1720.96 L945.187 1720.96 L945.469 1720.96 L945.469 1720.96 L945.187 1720.96 L945.187 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="945.187,1720.96 945.187,1720.96 945.469,1720.96 945.187,1720.96 "/>
<path clip-path="url(#clip322)" d="M945.469 1720.17 L945.469 1720.96 L945.751 1720.96 L945.751 1720.17 L945.469 1720.17 L945.469 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="945.469,1720.17 945.469,1720.96 945.751,1720.96 945.751,1720.17 945.469,1720.17 "/>
<path clip-path="url(#clip322)" d="M945.751 1720.37 L945.751 1720.96 L946.032 1720.96 L946.032 1720.37 L945.751 1720.37 L945.751 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="945.751,1720.37 945.751,1720.96 946.032,1720.96 946.032,1720.37 945.751,1720.37 "/>
<path clip-path="url(#clip322)" d="M946.032 1720.76 L946.032 1720.96 L946.314 1720.96 L946.314 1720.76 L946.032 1720.76 L946.032 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="946.032,1720.76 946.032,1720.96 946.314,1720.96 946.314,1720.76 946.032,1720.76 "/>
<path clip-path="url(#clip322)" d="M946.314 1720.76 L946.314 1720.96 L946.596 1720.96 L946.596 1720.76 L946.314 1720.76 L946.314 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="946.314,1720.76 946.314,1720.96 946.596,1720.96 946.596,1720.76 946.314,1720.76 "/>
<path clip-path="url(#clip322)" d="M946.596 1720.76 L946.596 1720.96 L946.878 1720.96 L946.878 1720.76 L946.596 1720.76 L946.596 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="946.596,1720.76 946.596,1720.96 946.878,1720.96 946.878,1720.76 946.596,1720.76 "/>
<path clip-path="url(#clip322)" d="M946.878 1720.76 L946.878 1720.96 L947.159 1720.96 L947.159 1720.76 L946.878 1720.76 L946.878 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="946.878,1720.76 946.878,1720.96 947.159,1720.96 947.159,1720.76 946.878,1720.76 "/>
<path clip-path="url(#clip322)" d="M947.159 1720.76 L947.159 1720.96 L947.441 1720.96 L947.441 1720.76 L947.159 1720.76 L947.159 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="947.159,1720.76 947.159,1720.96 947.441,1720.96 947.441,1720.76 947.159,1720.76 "/>
<path clip-path="url(#clip322)" d="M947.441 1720.37 L947.441 1720.96 L947.723 1720.96 L947.723 1720.37 L947.441 1720.37 L947.441 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="947.441,1720.37 947.441,1720.96 947.723,1720.96 947.723,1720.37 947.441,1720.37 "/>
<path clip-path="url(#clip322)" d="M947.723 1720.76 L947.723 1720.96 L948.004 1720.96 L948.004 1720.76 L947.723 1720.76 L947.723 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="947.723,1720.76 947.723,1720.96 948.004,1720.96 948.004,1720.76 947.723,1720.76 "/>
<path clip-path="url(#clip322)" d="M948.004 1720.56 L948.004 1720.96 L948.286 1720.96 L948.286 1720.56 L948.004 1720.56 L948.004 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="948.004,1720.56 948.004,1720.96 948.286,1720.96 948.286,1720.56 948.004,1720.56 "/>
<path clip-path="url(#clip322)" d="M948.286 1720.56 L948.286 1720.96 L948.568 1720.96 L948.568 1720.56 L948.286 1720.56 L948.286 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="948.286,1720.56 948.286,1720.96 948.568,1720.96 948.568,1720.56 948.286,1720.56 "/>
<path clip-path="url(#clip322)" d="M948.568 1720.76 L948.568 1720.96 L948.85 1720.96 L948.85 1720.76 L948.568 1720.76 L948.568 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="948.568,1720.76 948.568,1720.96 948.85,1720.96 948.85,1720.76 948.568,1720.76 "/>
<path clip-path="url(#clip322)" d="M948.85 1720.96 L948.85 1720.96 L949.131 1720.96 L949.131 1720.96 L948.85 1720.96 L948.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="948.85,1720.96 948.85,1720.96 949.131,1720.96 948.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M949.131 1720.76 L949.131 1720.96 L949.413 1720.96 L949.413 1720.76 L949.131 1720.76 L949.131 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="949.131,1720.76 949.131,1720.96 949.413,1720.96 949.413,1720.76 949.131,1720.76 "/>
<path clip-path="url(#clip322)" d="M949.413 1720.37 L949.413 1720.96 L949.695 1720.96 L949.695 1720.37 L949.413 1720.37 L949.413 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="949.413,1720.37 949.413,1720.96 949.695,1720.96 949.695,1720.37 949.413,1720.37 "/>
<path clip-path="url(#clip322)" d="M949.695 1720.96 L949.695 1720.96 L949.977 1720.96 L949.977 1720.96 L949.695 1720.96 L949.695 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="949.695,1720.96 949.695,1720.96 949.977,1720.96 949.695,1720.96 "/>
<path clip-path="url(#clip322)" d="M949.977 1720.76 L949.977 1720.96 L950.258 1720.96 L950.258 1720.76 L949.977 1720.76 L949.977 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="949.977,1720.76 949.977,1720.96 950.258,1720.96 950.258,1720.76 949.977,1720.76 "/>
<path clip-path="url(#clip322)" d="M950.258 1720.76 L950.258 1720.96 L950.54 1720.96 L950.54 1720.76 L950.258 1720.76 L950.258 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="950.258,1720.76 950.258,1720.96 950.54,1720.96 950.54,1720.76 950.258,1720.76 "/>
<path clip-path="url(#clip322)" d="M950.54 1720.76 L950.54 1720.96 L950.822 1720.96 L950.822 1720.76 L950.54 1720.76 L950.54 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="950.54,1720.76 950.54,1720.96 950.822,1720.96 950.822,1720.76 950.54,1720.76 "/>
<path clip-path="url(#clip322)" d="M950.822 1720.76 L950.822 1720.96 L951.103 1720.96 L951.103 1720.76 L950.822 1720.76 L950.822 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="950.822,1720.76 950.822,1720.96 951.103,1720.96 951.103,1720.76 950.822,1720.76 "/>
<path clip-path="url(#clip322)" d="M951.103 1720.96 L951.103 1720.96 L951.385 1720.96 L951.385 1720.96 L951.103 1720.96 L951.103 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="951.103,1720.96 951.103,1720.96 951.385,1720.96 951.103,1720.96 "/>
<path clip-path="url(#clip322)" d="M951.385 1720.76 L951.385 1720.96 L951.667 1720.96 L951.667 1720.76 L951.385 1720.76 L951.385 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="951.385,1720.76 951.385,1720.96 951.667,1720.96 951.667,1720.76 951.385,1720.76 "/>
<path clip-path="url(#clip322)" d="M951.667 1720.96 L951.667 1720.96 L951.949 1720.96 L951.949 1720.96 L951.667 1720.96 L951.667 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="951.667,1720.96 951.667,1720.96 951.949,1720.96 951.667,1720.96 "/>
<path clip-path="url(#clip322)" d="M951.949 1720.56 L951.949 1720.96 L952.23 1720.96 L952.23 1720.56 L951.949 1720.56 L951.949 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="951.949,1720.56 951.949,1720.96 952.23,1720.96 952.23,1720.56 951.949,1720.56 "/>
<path clip-path="url(#clip322)" d="M952.23 1720.76 L952.23 1720.96 L952.512 1720.96 L952.512 1720.76 L952.23 1720.76 L952.23 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="952.23,1720.76 952.23,1720.96 952.512,1720.96 952.512,1720.76 952.23,1720.76 "/>
<path clip-path="url(#clip322)" d="M952.512 1720.76 L952.512 1720.96 L952.794 1720.96 L952.794 1720.76 L952.512 1720.76 L952.512 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="952.512,1720.76 952.512,1720.96 952.794,1720.96 952.794,1720.76 952.512,1720.76 "/>
<path clip-path="url(#clip322)" d="M952.794 1720.96 L952.794 1720.96 L953.076 1720.96 L953.076 1720.96 L952.794 1720.96 L952.794 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="952.794,1720.96 952.794,1720.96 953.076,1720.96 952.794,1720.96 "/>
<path clip-path="url(#clip322)" d="M953.076 1720.76 L953.076 1720.96 L953.357 1720.96 L953.357 1720.76 L953.076 1720.76 L953.076 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="953.076,1720.76 953.076,1720.96 953.357,1720.96 953.357,1720.76 953.076,1720.76 "/>
<path clip-path="url(#clip322)" d="M953.357 1720.96 L953.357 1720.96 L953.639 1720.96 L953.639 1720.96 L953.357 1720.96 L953.357 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="953.357,1720.96 953.357,1720.96 953.639,1720.96 953.357,1720.96 "/>
<path clip-path="url(#clip322)" d="M953.639 1720.96 L953.639 1720.96 L953.921 1720.96 L953.921 1720.96 L953.639 1720.96 L953.639 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="953.639,1720.96 953.639,1720.96 953.921,1720.96 953.639,1720.96 "/>
<path clip-path="url(#clip322)" d="M953.921 1720.76 L953.921 1720.96 L954.202 1720.96 L954.202 1720.76 L953.921 1720.76 L953.921 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="953.921,1720.76 953.921,1720.96 954.202,1720.96 954.202,1720.76 953.921,1720.76 "/>
<path clip-path="url(#clip322)" d="M954.202 1720.96 L954.202 1720.96 L954.484 1720.96 L954.484 1720.96 L954.202 1720.96 L954.202 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="954.202,1720.96 954.202,1720.96 954.484,1720.96 954.202,1720.96 "/>
<path clip-path="url(#clip322)" d="M954.484 1720.76 L954.484 1720.96 L954.766 1720.96 L954.766 1720.76 L954.484 1720.76 L954.484 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="954.484,1720.76 954.484,1720.96 954.766,1720.96 954.766,1720.76 954.484,1720.76 "/>
<path clip-path="url(#clip322)" d="M954.766 1720.96 L954.766 1720.96 L955.048 1720.96 L955.048 1720.96 L954.766 1720.96 L954.766 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="954.766,1720.96 954.766,1720.96 955.048,1720.96 954.766,1720.96 "/>
<path clip-path="url(#clip322)" d="M955.048 1720.96 L955.048 1720.96 L955.329 1720.96 L955.329 1720.96 L955.048 1720.96 L955.048 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="955.048,1720.96 955.048,1720.96 955.329,1720.96 955.048,1720.96 "/>
<path clip-path="url(#clip322)" d="M955.329 1720.76 L955.329 1720.96 L955.611 1720.96 L955.611 1720.76 L955.329 1720.76 L955.329 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="955.329,1720.76 955.329,1720.96 955.611,1720.96 955.611,1720.76 955.329,1720.76 "/>
<path clip-path="url(#clip322)" d="M955.611 1720.76 L955.611 1720.96 L955.893 1720.96 L955.893 1720.76 L955.611 1720.76 L955.611 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="955.611,1720.76 955.611,1720.96 955.893,1720.96 955.893,1720.76 955.611,1720.76 "/>
<path clip-path="url(#clip322)" d="M955.893 1720.56 L955.893 1720.96 L956.175 1720.96 L956.175 1720.56 L955.893 1720.56 L955.893 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="955.893,1720.56 955.893,1720.96 956.175,1720.96 956.175,1720.56 955.893,1720.56 "/>
<path clip-path="url(#clip322)" d="M956.175 1720.96 L956.175 1720.96 L956.456 1720.96 L956.456 1720.96 L956.175 1720.96 L956.175 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="956.175,1720.96 956.175,1720.96 956.456,1720.96 956.175,1720.96 "/>
<path clip-path="url(#clip322)" d="M956.456 1720.56 L956.456 1720.96 L956.738 1720.96 L956.738 1720.56 L956.456 1720.56 L956.456 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="956.456,1720.56 956.456,1720.96 956.738,1720.96 956.738,1720.56 956.456,1720.56 "/>
<path clip-path="url(#clip322)" d="M956.738 1720.76 L956.738 1720.96 L957.02 1720.96 L957.02 1720.76 L956.738 1720.76 L956.738 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="956.738,1720.76 956.738,1720.96 957.02,1720.96 957.02,1720.76 956.738,1720.76 "/>
<path clip-path="url(#clip322)" d="M957.02 1720.96 L957.02 1720.96 L957.301 1720.96 L957.301 1720.96 L957.02 1720.96 L957.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="957.02,1720.96 957.02,1720.96 957.301,1720.96 957.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M957.301 1720.56 L957.301 1720.96 L957.583 1720.96 L957.583 1720.56 L957.301 1720.56 L957.301 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="957.301,1720.56 957.301,1720.96 957.583,1720.96 957.583,1720.56 957.301,1720.56 "/>
<path clip-path="url(#clip322)" d="M957.583 1720.76 L957.583 1720.96 L957.865 1720.96 L957.865 1720.76 L957.583 1720.76 L957.583 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="957.583,1720.76 957.583,1720.96 957.865,1720.96 957.865,1720.76 957.583,1720.76 "/>
<path clip-path="url(#clip322)" d="M957.865 1720.96 L957.865 1720.96 L958.147 1720.96 L958.147 1720.96 L957.865 1720.96 L957.865 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="957.865,1720.96 957.865,1720.96 958.147,1720.96 957.865,1720.96 "/>
<path clip-path="url(#clip322)" d="M958.147 1720.17 L958.147 1720.96 L958.428 1720.96 L958.428 1720.17 L958.147 1720.17 L958.147 1720.17  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="958.147,1720.17 958.147,1720.96 958.428,1720.96 958.428,1720.17 958.147,1720.17 "/>
<path clip-path="url(#clip322)" d="M958.428 1720.96 L958.428 1720.96 L958.71 1720.96 L958.71 1720.96 L958.428 1720.96 L958.428 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="958.428,1720.96 958.428,1720.96 958.71,1720.96 958.428,1720.96 "/>
<path clip-path="url(#clip322)" d="M958.71 1720.56 L958.71 1720.96 L958.992 1720.96 L958.992 1720.56 L958.71 1720.56 L958.71 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="958.71,1720.56 958.71,1720.96 958.992,1720.96 958.992,1720.56 958.71,1720.56 "/>
<path clip-path="url(#clip322)" d="M958.992 1720.56 L958.992 1720.96 L959.273 1720.96 L959.273 1720.56 L958.992 1720.56 L958.992 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="958.992,1720.56 958.992,1720.96 959.273,1720.96 959.273,1720.56 958.992,1720.56 "/>
<path clip-path="url(#clip322)" d="M959.273 1720.76 L959.273 1720.96 L959.555 1720.96 L959.555 1720.76 L959.273 1720.76 L959.273 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="959.273,1720.76 959.273,1720.96 959.555,1720.96 959.555,1720.76 959.273,1720.76 "/>
<path clip-path="url(#clip322)" d="M959.555 1720.96 L959.555 1720.96 L959.837 1720.96 L959.837 1720.96 L959.555 1720.96 L959.555 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="959.555,1720.96 959.555,1720.96 959.837,1720.96 959.555,1720.96 "/>
<path clip-path="url(#clip322)" d="M959.837 1720.56 L959.837 1720.96 L960.119 1720.96 L960.119 1720.56 L959.837 1720.56 L959.837 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="959.837,1720.56 959.837,1720.96 960.119,1720.96 960.119,1720.56 959.837,1720.56 "/>
<path clip-path="url(#clip322)" d="M960.119 1720.96 L960.119 1720.96 L960.4 1720.96 L960.4 1720.96 L960.119 1720.96 L960.119 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="960.119,1720.96 960.119,1720.96 960.4,1720.96 960.119,1720.96 "/>
<path clip-path="url(#clip322)" d="M960.4 1720.96 L960.4 1720.96 L960.682 1720.96 L960.682 1720.96 L960.4 1720.96 L960.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="960.4,1720.96 960.4,1720.96 960.682,1720.96 960.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M960.682 1720.76 L960.682 1720.96 L960.964 1720.96 L960.964 1720.76 L960.682 1720.76 L960.682 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="960.682,1720.76 960.682,1720.96 960.964,1720.96 960.964,1720.76 960.682,1720.76 "/>
<path clip-path="url(#clip322)" d="M960.964 1720.96 L960.964 1720.96 L961.246 1720.96 L961.246 1720.96 L960.964 1720.96 L960.964 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="960.964,1720.96 960.964,1720.96 961.246,1720.96 960.964,1720.96 "/>
<path clip-path="url(#clip322)" d="M961.246 1720.56 L961.246 1720.96 L961.527 1720.96 L961.527 1720.56 L961.246 1720.56 L961.246 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="961.246,1720.56 961.246,1720.96 961.527,1720.96 961.527,1720.56 961.246,1720.56 "/>
<path clip-path="url(#clip322)" d="M961.527 1720.96 L961.527 1720.96 L961.809 1720.96 L961.809 1720.96 L961.527 1720.96 L961.527 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="961.527,1720.96 961.527,1720.96 961.809,1720.96 961.527,1720.96 "/>
<path clip-path="url(#clip322)" d="M961.809 1720.76 L961.809 1720.96 L962.091 1720.96 L962.091 1720.76 L961.809 1720.76 L961.809 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="961.809,1720.76 961.809,1720.96 962.091,1720.96 962.091,1720.76 961.809,1720.76 "/>
<path clip-path="url(#clip322)" d="M962.091 1720.76 L962.091 1720.96 L962.372 1720.96 L962.372 1720.76 L962.091 1720.76 L962.091 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="962.091,1720.76 962.091,1720.96 962.372,1720.96 962.372,1720.76 962.091,1720.76 "/>
<path clip-path="url(#clip322)" d="M962.372 1720.96 L962.372 1720.96 L962.654 1720.96 L962.654 1720.96 L962.372 1720.96 L962.372 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="962.372,1720.96 962.372,1720.96 962.654,1720.96 962.372,1720.96 "/>
<path clip-path="url(#clip322)" d="M962.654 1720.56 L962.654 1720.96 L962.936 1720.96 L962.936 1720.56 L962.654 1720.56 L962.654 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="962.654,1720.56 962.654,1720.96 962.936,1720.96 962.936,1720.56 962.654,1720.56 "/>
<path clip-path="url(#clip322)" d="M962.936 1720.76 L962.936 1720.96 L963.218 1720.96 L963.218 1720.76 L962.936 1720.76 L962.936 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="962.936,1720.76 962.936,1720.96 963.218,1720.96 963.218,1720.76 962.936,1720.76 "/>
<path clip-path="url(#clip322)" d="M963.218 1720.56 L963.218 1720.96 L963.499 1720.96 L963.499 1720.56 L963.218 1720.56 L963.218 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="963.218,1720.56 963.218,1720.96 963.499,1720.96 963.499,1720.56 963.218,1720.56 "/>
<path clip-path="url(#clip322)" d="M963.499 1720.56 L963.499 1720.96 L963.781 1720.96 L963.781 1720.56 L963.499 1720.56 L963.499 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="963.499,1720.56 963.499,1720.96 963.781,1720.96 963.781,1720.56 963.499,1720.56 "/>
<path clip-path="url(#clip322)" d="M963.781 1720.56 L963.781 1720.96 L964.063 1720.96 L964.063 1720.56 L963.781 1720.56 L963.781 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="963.781,1720.56 963.781,1720.96 964.063,1720.96 964.063,1720.56 963.781,1720.56 "/>
<path clip-path="url(#clip322)" d="M964.063 1720.96 L964.063 1720.96 L964.345 1720.96 L964.345 1720.96 L964.063 1720.96 L964.063 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="964.063,1720.96 964.063,1720.96 964.345,1720.96 964.063,1720.96 "/>
<path clip-path="url(#clip322)" d="M964.345 1720.96 L964.345 1720.96 L964.626 1720.96 L964.626 1720.96 L964.345 1720.96 L964.345 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="964.345,1720.96 964.345,1720.96 964.626,1720.96 964.345,1720.96 "/>
<path clip-path="url(#clip322)" d="M964.626 1720.76 L964.626 1720.96 L964.908 1720.96 L964.908 1720.76 L964.626 1720.76 L964.626 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="964.626,1720.76 964.626,1720.96 964.908,1720.96 964.908,1720.76 964.626,1720.76 "/>
<path clip-path="url(#clip322)" d="M964.908 1720.76 L964.908 1720.96 L965.19 1720.96 L965.19 1720.76 L964.908 1720.76 L964.908 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="964.908,1720.76 964.908,1720.96 965.19,1720.96 965.19,1720.76 964.908,1720.76 "/>
<path clip-path="url(#clip322)" d="M965.19 1720.37 L965.19 1720.96 L965.471 1720.96 L965.471 1720.37 L965.19 1720.37 L965.19 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="965.19,1720.37 965.19,1720.96 965.471,1720.96 965.471,1720.37 965.19,1720.37 "/>
<path clip-path="url(#clip322)" d="M965.471 1720.56 L965.471 1720.96 L965.753 1720.96 L965.753 1720.56 L965.471 1720.56 L965.471 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="965.471,1720.56 965.471,1720.96 965.753,1720.96 965.753,1720.56 965.471,1720.56 "/>
<path clip-path="url(#clip322)" d="M965.753 1720.76 L965.753 1720.96 L966.035 1720.96 L966.035 1720.76 L965.753 1720.76 L965.753 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="965.753,1720.76 965.753,1720.96 966.035,1720.96 966.035,1720.76 965.753,1720.76 "/>
<path clip-path="url(#clip322)" d="M966.035 1720.76 L966.035 1720.96 L966.317 1720.96 L966.317 1720.76 L966.035 1720.76 L966.035 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="966.035,1720.76 966.035,1720.96 966.317,1720.96 966.317,1720.76 966.035,1720.76 "/>
<path clip-path="url(#clip322)" d="M966.317 1720.76 L966.317 1720.96 L966.598 1720.96 L966.598 1720.76 L966.317 1720.76 L966.317 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="966.317,1720.76 966.317,1720.96 966.598,1720.96 966.598,1720.76 966.317,1720.76 "/>
<path clip-path="url(#clip322)" d="M966.598 1720.76 L966.598 1720.96 L966.88 1720.96 L966.88 1720.76 L966.598 1720.76 L966.598 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="966.598,1720.76 966.598,1720.96 966.88,1720.96 966.88,1720.76 966.598,1720.76 "/>
<path clip-path="url(#clip322)" d="M966.88 1720.76 L966.88 1720.96 L967.162 1720.96 L967.162 1720.76 L966.88 1720.76 L966.88 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="966.88,1720.76 966.88,1720.96 967.162,1720.96 967.162,1720.76 966.88,1720.76 "/>
<path clip-path="url(#clip322)" d="M967.162 1720.56 L967.162 1720.96 L967.444 1720.96 L967.444 1720.56 L967.162 1720.56 L967.162 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="967.162,1720.56 967.162,1720.96 967.444,1720.96 967.444,1720.56 967.162,1720.56 "/>
<path clip-path="url(#clip322)" d="M967.444 1720.96 L967.444 1720.96 L967.725 1720.96 L967.725 1720.96 L967.444 1720.96 L967.444 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="967.444,1720.96 967.444,1720.96 967.725,1720.96 967.444,1720.96 "/>
<path clip-path="url(#clip322)" d="M967.725 1720.56 L967.725 1720.96 L968.007 1720.96 L968.007 1720.56 L967.725 1720.56 L967.725 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="967.725,1720.56 967.725,1720.96 968.007,1720.96 968.007,1720.56 967.725,1720.56 "/>
<path clip-path="url(#clip322)" d="M968.007 1720.76 L968.007 1720.96 L968.289 1720.96 L968.289 1720.76 L968.007 1720.76 L968.007 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="968.007,1720.76 968.007,1720.96 968.289,1720.96 968.289,1720.76 968.007,1720.76 "/>
<path clip-path="url(#clip322)" d="M968.289 1720.76 L968.289 1720.96 L968.57 1720.96 L968.57 1720.76 L968.289 1720.76 L968.289 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="968.289,1720.76 968.289,1720.96 968.57,1720.96 968.57,1720.76 968.289,1720.76 "/>
<path clip-path="url(#clip322)" d="M968.57 1720.76 L968.57 1720.96 L968.852 1720.96 L968.852 1720.76 L968.57 1720.76 L968.57 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="968.57,1720.76 968.57,1720.96 968.852,1720.96 968.852,1720.76 968.57,1720.76 "/>
<path clip-path="url(#clip322)" d="M968.852 1720.56 L968.852 1720.96 L969.134 1720.96 L969.134 1720.56 L968.852 1720.56 L968.852 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="968.852,1720.56 968.852,1720.96 969.134,1720.96 969.134,1720.56 968.852,1720.56 "/>
<path clip-path="url(#clip322)" d="M969.134 1720.96 L969.134 1720.96 L969.416 1720.96 L969.416 1720.96 L969.134 1720.96 L969.134 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="969.134,1720.96 969.134,1720.96 969.416,1720.96 969.134,1720.96 "/>
<path clip-path="url(#clip322)" d="M969.416 1720.76 L969.416 1720.96 L969.697 1720.96 L969.697 1720.76 L969.416 1720.76 L969.416 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="969.416,1720.76 969.416,1720.96 969.697,1720.96 969.697,1720.76 969.416,1720.76 "/>
<path clip-path="url(#clip322)" d="M969.697 1720.96 L969.697 1720.96 L969.979 1720.96 L969.979 1720.96 L969.697 1720.96 L969.697 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="969.697,1720.96 969.697,1720.96 969.979,1720.96 969.697,1720.96 "/>
<path clip-path="url(#clip322)" d="M969.979 1720.76 L969.979 1720.96 L970.261 1720.96 L970.261 1720.76 L969.979 1720.76 L969.979 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="969.979,1720.76 969.979,1720.96 970.261,1720.96 970.261,1720.76 969.979,1720.76 "/>
<path clip-path="url(#clip322)" d="M970.261 1720.76 L970.261 1720.96 L970.543 1720.96 L970.543 1720.76 L970.261 1720.76 L970.261 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="970.261,1720.76 970.261,1720.96 970.543,1720.96 970.543,1720.76 970.261,1720.76 "/>
<path clip-path="url(#clip322)" d="M970.543 1720.96 L970.543 1720.96 L970.824 1720.96 L970.824 1720.96 L970.543 1720.96 L970.543 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="970.543,1720.96 970.543,1720.96 970.824,1720.96 970.543,1720.96 "/>
<path clip-path="url(#clip322)" d="M970.824 1720.37 L970.824 1720.96 L971.106 1720.96 L971.106 1720.37 L970.824 1720.37 L970.824 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="970.824,1720.37 970.824,1720.96 971.106,1720.96 971.106,1720.37 970.824,1720.37 "/>
<path clip-path="url(#clip322)" d="M971.106 1720.56 L971.106 1720.96 L971.388 1720.96 L971.388 1720.56 L971.106 1720.56 L971.106 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="971.106,1720.56 971.106,1720.96 971.388,1720.96 971.388,1720.56 971.106,1720.56 "/>
<path clip-path="url(#clip322)" d="M971.388 1720.37 L971.388 1720.96 L971.669 1720.96 L971.669 1720.37 L971.388 1720.37 L971.388 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="971.388,1720.37 971.388,1720.96 971.669,1720.96 971.669,1720.37 971.388,1720.37 "/>
<path clip-path="url(#clip322)" d="M971.669 1720.96 L971.669 1720.96 L971.951 1720.96 L971.951 1720.96 L971.669 1720.96 L971.669 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="971.669,1720.96 971.669,1720.96 971.951,1720.96 971.669,1720.96 "/>
<path clip-path="url(#clip322)" d="M971.951 1720.96 L971.951 1720.96 L972.233 1720.96 L972.233 1720.96 L971.951 1720.96 L971.951 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="971.951,1720.96 971.951,1720.96 972.233,1720.96 971.951,1720.96 "/>
<path clip-path="url(#clip322)" d="M972.233 1720.56 L972.233 1720.96 L972.515 1720.96 L972.515 1720.56 L972.233 1720.56 L972.233 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="972.233,1720.56 972.233,1720.96 972.515,1720.96 972.515,1720.56 972.233,1720.56 "/>
<path clip-path="url(#clip322)" d="M972.515 1720.96 L972.515 1720.96 L972.796 1720.96 L972.796 1720.96 L972.515 1720.96 L972.515 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="972.515,1720.96 972.515,1720.96 972.796,1720.96 972.515,1720.96 "/>
<path clip-path="url(#clip322)" d="M972.796 1720.76 L972.796 1720.96 L973.078 1720.96 L973.078 1720.76 L972.796 1720.76 L972.796 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="972.796,1720.76 972.796,1720.96 973.078,1720.96 973.078,1720.76 972.796,1720.76 "/>
<path clip-path="url(#clip322)" d="M973.078 1720.76 L973.078 1720.96 L973.36 1720.96 L973.36 1720.76 L973.078 1720.76 L973.078 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="973.078,1720.76 973.078,1720.96 973.36,1720.96 973.36,1720.76 973.078,1720.76 "/>
<path clip-path="url(#clip322)" d="M973.36 1720.56 L973.36 1720.96 L973.642 1720.96 L973.642 1720.56 L973.36 1720.56 L973.36 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="973.36,1720.56 973.36,1720.96 973.642,1720.96 973.642,1720.56 973.36,1720.56 "/>
<path clip-path="url(#clip322)" d="M973.642 1720.96 L973.642 1720.96 L973.923 1720.96 L973.923 1720.96 L973.642 1720.96 L973.642 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="973.642,1720.96 973.642,1720.96 973.923,1720.96 973.642,1720.96 "/>
<path clip-path="url(#clip322)" d="M973.923 1720.76 L973.923 1720.96 L974.205 1720.96 L974.205 1720.76 L973.923 1720.76 L973.923 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="973.923,1720.76 973.923,1720.96 974.205,1720.96 974.205,1720.76 973.923,1720.76 "/>
<path clip-path="url(#clip322)" d="M974.205 1720.96 L974.205 1720.96 L974.487 1720.96 L974.487 1720.96 L974.205 1720.96 L974.205 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="974.205,1720.96 974.205,1720.96 974.487,1720.96 974.205,1720.96 "/>
<path clip-path="url(#clip322)" d="M974.487 1720.96 L974.487 1720.96 L974.768 1720.96 L974.768 1720.96 L974.487 1720.96 L974.487 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="974.487,1720.96 974.487,1720.96 974.768,1720.96 974.487,1720.96 "/>
<path clip-path="url(#clip322)" d="M974.768 1720.96 L974.768 1720.96 L975.05 1720.96 L975.05 1720.96 L974.768 1720.96 L974.768 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="974.768,1720.96 974.768,1720.96 975.05,1720.96 974.768,1720.96 "/>
<path clip-path="url(#clip322)" d="M975.05 1720.56 L975.05 1720.96 L975.332 1720.96 L975.332 1720.56 L975.05 1720.56 L975.05 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="975.05,1720.56 975.05,1720.96 975.332,1720.96 975.332,1720.56 975.05,1720.56 "/>
<path clip-path="url(#clip322)" d="M975.332 1720.76 L975.332 1720.96 L975.614 1720.96 L975.614 1720.76 L975.332 1720.76 L975.332 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="975.332,1720.76 975.332,1720.96 975.614,1720.96 975.614,1720.76 975.332,1720.76 "/>
<path clip-path="url(#clip322)" d="M975.614 1720.56 L975.614 1720.96 L975.895 1720.96 L975.895 1720.56 L975.614 1720.56 L975.614 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="975.614,1720.56 975.614,1720.96 975.895,1720.96 975.895,1720.56 975.614,1720.56 "/>
<path clip-path="url(#clip322)" d="M975.895 1720.76 L975.895 1720.96 L976.177 1720.96 L976.177 1720.76 L975.895 1720.76 L975.895 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="975.895,1720.76 975.895,1720.96 976.177,1720.96 976.177,1720.76 975.895,1720.76 "/>
<path clip-path="url(#clip322)" d="M976.177 1720.96 L976.177 1720.96 L976.459 1720.96 L976.459 1720.96 L976.177 1720.96 L976.177 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="976.177,1720.96 976.177,1720.96 976.459,1720.96 976.177,1720.96 "/>
<path clip-path="url(#clip322)" d="M976.459 1720.76 L976.459 1720.96 L976.74 1720.96 L976.74 1720.76 L976.459 1720.76 L976.459 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="976.459,1720.76 976.459,1720.96 976.74,1720.96 976.74,1720.76 976.459,1720.76 "/>
<path clip-path="url(#clip322)" d="M976.74 1720.96 L976.74 1720.96 L977.022 1720.96 L977.022 1720.96 L976.74 1720.96 L976.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="976.74,1720.96 976.74,1720.96 977.022,1720.96 976.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M977.022 1720.96 L977.022 1720.96 L977.304 1720.96 L977.304 1720.96 L977.022 1720.96 L977.022 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="977.022,1720.96 977.022,1720.96 977.304,1720.96 977.022,1720.96 "/>
<path clip-path="url(#clip322)" d="M977.304 1720.96 L977.304 1720.96 L977.586 1720.96 L977.586 1720.96 L977.304 1720.96 L977.304 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="977.304,1720.96 977.304,1720.96 977.586,1720.96 977.304,1720.96 "/>
<path clip-path="url(#clip322)" d="M977.586 1720.76 L977.586 1720.96 L977.867 1720.96 L977.867 1720.76 L977.586 1720.76 L977.586 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="977.586,1720.76 977.586,1720.96 977.867,1720.96 977.867,1720.76 977.586,1720.76 "/>
<path clip-path="url(#clip322)" d="M977.867 1720.96 L977.867 1720.96 L978.149 1720.96 L978.149 1720.96 L977.867 1720.96 L977.867 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="977.867,1720.96 977.867,1720.96 978.149,1720.96 977.867,1720.96 "/>
<path clip-path="url(#clip322)" d="M978.149 1720.37 L978.149 1720.96 L978.431 1720.96 L978.431 1720.37 L978.149 1720.37 L978.149 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="978.149,1720.37 978.149,1720.96 978.431,1720.96 978.431,1720.37 978.149,1720.37 "/>
<path clip-path="url(#clip322)" d="M978.431 1720.56 L978.431 1720.96 L978.713 1720.96 L978.713 1720.56 L978.431 1720.56 L978.431 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="978.431,1720.56 978.431,1720.96 978.713,1720.96 978.713,1720.56 978.431,1720.56 "/>
<path clip-path="url(#clip322)" d="M978.713 1720.76 L978.713 1720.96 L978.994 1720.96 L978.994 1720.76 L978.713 1720.76 L978.713 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="978.713,1720.76 978.713,1720.96 978.994,1720.96 978.994,1720.76 978.713,1720.76 "/>
<path clip-path="url(#clip322)" d="M978.994 1720.76 L978.994 1720.96 L979.276 1720.96 L979.276 1720.76 L978.994 1720.76 L978.994 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="978.994,1720.76 978.994,1720.96 979.276,1720.96 979.276,1720.76 978.994,1720.76 "/>
<path clip-path="url(#clip322)" d="M979.276 1720.76 L979.276 1720.96 L979.558 1720.96 L979.558 1720.76 L979.276 1720.76 L979.276 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="979.276,1720.76 979.276,1720.96 979.558,1720.96 979.558,1720.76 979.276,1720.76 "/>
<path clip-path="url(#clip322)" d="M979.558 1720.76 L979.558 1720.96 L979.839 1720.96 L979.839 1720.76 L979.558 1720.76 L979.558 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="979.558,1720.76 979.558,1720.96 979.839,1720.96 979.839,1720.76 979.558,1720.76 "/>
<path clip-path="url(#clip322)" d="M979.839 1720.96 L979.839 1720.96 L980.121 1720.96 L980.121 1720.96 L979.839 1720.96 L979.839 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="979.839,1720.96 979.839,1720.96 980.121,1720.96 979.839,1720.96 "/>
<path clip-path="url(#clip322)" d="M980.121 1720.76 L980.121 1720.96 L980.403 1720.96 L980.403 1720.76 L980.121 1720.76 L980.121 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="980.121,1720.76 980.121,1720.96 980.403,1720.96 980.403,1720.76 980.121,1720.76 "/>
<path clip-path="url(#clip322)" d="M980.403 1720.96 L980.403 1720.96 L980.685 1720.96 L980.685 1720.96 L980.403 1720.96 L980.403 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="980.403,1720.96 980.403,1720.96 980.685,1720.96 980.403,1720.96 "/>
<path clip-path="url(#clip322)" d="M980.685 1720.76 L980.685 1720.96 L980.966 1720.96 L980.966 1720.76 L980.685 1720.76 L980.685 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="980.685,1720.76 980.685,1720.96 980.966,1720.96 980.966,1720.76 980.685,1720.76 "/>
<path clip-path="url(#clip322)" d="M980.966 1720.96 L980.966 1720.96 L981.248 1720.96 L981.248 1720.96 L980.966 1720.96 L980.966 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="980.966,1720.96 980.966,1720.96 981.248,1720.96 980.966,1720.96 "/>
<path clip-path="url(#clip322)" d="M981.248 1720.96 L981.248 1720.96 L981.53 1720.96 L981.53 1720.96 L981.248 1720.96 L981.248 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="981.248,1720.96 981.248,1720.96 981.53,1720.96 981.248,1720.96 "/>
<path clip-path="url(#clip322)" d="M981.53 1720.76 L981.53 1720.96 L981.812 1720.96 L981.812 1720.76 L981.53 1720.76 L981.53 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="981.53,1720.76 981.53,1720.96 981.812,1720.96 981.812,1720.76 981.53,1720.76 "/>
<path clip-path="url(#clip322)" d="M981.812 1720.96 L981.812 1720.96 L982.093 1720.96 L982.093 1720.96 L981.812 1720.96 L981.812 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="981.812,1720.96 981.812,1720.96 982.093,1720.96 981.812,1720.96 "/>
<path clip-path="url(#clip322)" d="M982.093 1720.96 L982.093 1720.96 L982.375 1720.96 L982.375 1720.96 L982.093 1720.96 L982.093 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="982.093,1720.96 982.093,1720.96 982.375,1720.96 982.093,1720.96 "/>
<path clip-path="url(#clip322)" d="M982.375 1720.96 L982.375 1720.96 L982.657 1720.96 L982.657 1720.96 L982.375 1720.96 L982.375 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="982.375,1720.96 982.375,1720.96 982.657,1720.96 982.375,1720.96 "/>
<path clip-path="url(#clip322)" d="M982.657 1720.96 L982.657 1720.96 L982.938 1720.96 L982.938 1720.96 L982.657 1720.96 L982.657 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="982.657,1720.96 982.657,1720.96 982.938,1720.96 982.657,1720.96 "/>
<path clip-path="url(#clip322)" d="M982.938 1720.96 L982.938 1720.96 L983.22 1720.96 L983.22 1720.96 L982.938 1720.96 L982.938 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="982.938,1720.96 982.938,1720.96 983.22,1720.96 982.938,1720.96 "/>
<path clip-path="url(#clip322)" d="M983.22 1720.96 L983.22 1720.96 L983.502 1720.96 L983.502 1720.96 L983.22 1720.96 L983.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="983.22,1720.96 983.22,1720.96 983.502,1720.96 983.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M983.502 1720.96 L983.502 1720.96 L983.784 1720.96 L983.784 1720.96 L983.502 1720.96 L983.502 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="983.502,1720.96 983.502,1720.96 983.784,1720.96 983.502,1720.96 "/>
<path clip-path="url(#clip322)" d="M983.784 1720.76 L983.784 1720.96 L984.065 1720.96 L984.065 1720.76 L983.784 1720.76 L983.784 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="983.784,1720.76 983.784,1720.96 984.065,1720.96 984.065,1720.76 983.784,1720.76 "/>
<path clip-path="url(#clip322)" d="M984.065 1720.56 L984.065 1720.96 L984.347 1720.96 L984.347 1720.56 L984.065 1720.56 L984.065 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="984.065,1720.56 984.065,1720.96 984.347,1720.96 984.347,1720.56 984.065,1720.56 "/>
<path clip-path="url(#clip322)" d="M984.347 1720.76 L984.347 1720.96 L984.629 1720.96 L984.629 1720.76 L984.347 1720.76 L984.347 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="984.347,1720.76 984.347,1720.96 984.629,1720.96 984.629,1720.76 984.347,1720.76 "/>
<path clip-path="url(#clip322)" d="M984.629 1720.96 L984.629 1720.96 L984.911 1720.96 L984.911 1720.96 L984.629 1720.96 L984.629 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="984.629,1720.96 984.629,1720.96 984.911,1720.96 984.629,1720.96 "/>
<path clip-path="url(#clip322)" d="M984.911 1720.56 L984.911 1720.96 L985.192 1720.96 L985.192 1720.56 L984.911 1720.56 L984.911 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="984.911,1720.56 984.911,1720.96 985.192,1720.96 985.192,1720.56 984.911,1720.56 "/>
<path clip-path="url(#clip322)" d="M985.192 1720.96 L985.192 1720.96 L985.474 1720.96 L985.474 1720.96 L985.192 1720.96 L985.192 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="985.192,1720.96 985.192,1720.96 985.474,1720.96 985.192,1720.96 "/>
<path clip-path="url(#clip322)" d="M985.474 1720.56 L985.474 1720.96 L985.756 1720.96 L985.756 1720.56 L985.474 1720.56 L985.474 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="985.474,1720.56 985.474,1720.96 985.756,1720.96 985.756,1720.56 985.474,1720.56 "/>
<path clip-path="url(#clip322)" d="M985.756 1720.76 L985.756 1720.96 L986.037 1720.96 L986.037 1720.76 L985.756 1720.76 L985.756 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="985.756,1720.76 985.756,1720.96 986.037,1720.96 986.037,1720.76 985.756,1720.76 "/>
<path clip-path="url(#clip322)" d="M986.037 1720.76 L986.037 1720.96 L986.319 1720.96 L986.319 1720.76 L986.037 1720.76 L986.037 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="986.037,1720.76 986.037,1720.96 986.319,1720.96 986.319,1720.76 986.037,1720.76 "/>
<path clip-path="url(#clip322)" d="M986.319 1720.37 L986.319 1720.96 L986.601 1720.96 L986.601 1720.37 L986.319 1720.37 L986.319 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="986.319,1720.37 986.319,1720.96 986.601,1720.96 986.601,1720.37 986.319,1720.37 "/>
<path clip-path="url(#clip322)" d="M986.601 1720.96 L986.601 1720.96 L986.883 1720.96 L986.883 1720.96 L986.601 1720.96 L986.601 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="986.601,1720.96 986.601,1720.96 986.883,1720.96 986.601,1720.96 "/>
<path clip-path="url(#clip322)" d="M986.883 1720.76 L986.883 1720.96 L987.164 1720.96 L987.164 1720.76 L986.883 1720.76 L986.883 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="986.883,1720.76 986.883,1720.96 987.164,1720.96 987.164,1720.76 986.883,1720.76 "/>
<path clip-path="url(#clip322)" d="M987.164 1720.96 L987.164 1720.96 L987.446 1720.96 L987.446 1720.96 L987.164 1720.96 L987.164 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="987.164,1720.96 987.164,1720.96 987.446,1720.96 987.164,1720.96 "/>
<path clip-path="url(#clip322)" d="M987.446 1720.96 L987.446 1720.96 L987.728 1720.96 L987.728 1720.96 L987.446 1720.96 L987.446 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="987.446,1720.96 987.446,1720.96 987.728,1720.96 987.446,1720.96 "/>
<path clip-path="url(#clip322)" d="M987.728 1720.96 L987.728 1720.96 L988.01 1720.96 L988.01 1720.96 L987.728 1720.96 L987.728 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="987.728,1720.96 987.728,1720.96 988.01,1720.96 987.728,1720.96 "/>
<path clip-path="url(#clip322)" d="M988.01 1720.96 L988.01 1720.96 L988.291 1720.96 L988.291 1720.96 L988.01 1720.96 L988.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="988.01,1720.96 988.01,1720.96 988.291,1720.96 988.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M988.291 1720.76 L988.291 1720.96 L988.573 1720.96 L988.573 1720.76 L988.291 1720.76 L988.291 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="988.291,1720.76 988.291,1720.96 988.573,1720.96 988.573,1720.76 988.291,1720.76 "/>
<path clip-path="url(#clip322)" d="M988.573 1720.76 L988.573 1720.96 L988.855 1720.96 L988.855 1720.76 L988.573 1720.76 L988.573 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="988.573,1720.76 988.573,1720.96 988.855,1720.96 988.855,1720.76 988.573,1720.76 "/>
<path clip-path="url(#clip322)" d="M988.855 1720.56 L988.855 1720.96 L989.136 1720.96 L989.136 1720.56 L988.855 1720.56 L988.855 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="988.855,1720.56 988.855,1720.96 989.136,1720.96 989.136,1720.56 988.855,1720.56 "/>
<path clip-path="url(#clip322)" d="M989.136 1720.96 L989.136 1720.96 L989.418 1720.96 L989.418 1720.96 L989.136 1720.96 L989.136 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="989.136,1720.96 989.136,1720.96 989.418,1720.96 989.136,1720.96 "/>
<path clip-path="url(#clip322)" d="M989.418 1720.96 L989.418 1720.96 L989.7 1720.96 L989.7 1720.96 L989.418 1720.96 L989.418 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="989.418,1720.96 989.418,1720.96 989.7,1720.96 989.418,1720.96 "/>
<path clip-path="url(#clip322)" d="M989.7 1720.96 L989.7 1720.96 L989.982 1720.96 L989.982 1720.96 L989.7 1720.96 L989.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="989.7,1720.96 989.7,1720.96 989.982,1720.96 989.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M989.982 1720.76 L989.982 1720.96 L990.263 1720.96 L990.263 1720.76 L989.982 1720.76 L989.982 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="989.982,1720.76 989.982,1720.96 990.263,1720.96 990.263,1720.76 989.982,1720.76 "/>
<path clip-path="url(#clip322)" d="M990.263 1720.96 L990.263 1720.96 L990.545 1720.96 L990.545 1720.96 L990.263 1720.96 L990.263 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="990.263,1720.96 990.263,1720.96 990.545,1720.96 990.263,1720.96 "/>
<path clip-path="url(#clip322)" d="M990.545 1720.76 L990.545 1720.96 L990.827 1720.96 L990.827 1720.76 L990.545 1720.76 L990.545 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="990.545,1720.76 990.545,1720.96 990.827,1720.96 990.827,1720.76 990.545,1720.76 "/>
<path clip-path="url(#clip322)" d="M990.827 1719.97 L990.827 1720.96 L991.108 1720.96 L991.108 1719.97 L990.827 1719.97 L990.827 1719.97  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="990.827,1719.97 990.827,1720.96 991.108,1720.96 991.108,1719.97 990.827,1719.97 "/>
<path clip-path="url(#clip322)" d="M991.108 1720.96 L991.108 1720.96 L991.39 1720.96 L991.39 1720.96 L991.108 1720.96 L991.108 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="991.108,1720.96 991.108,1720.96 991.39,1720.96 991.108,1720.96 "/>
<path clip-path="url(#clip322)" d="M991.39 1720.96 L991.39 1720.96 L991.672 1720.96 L991.672 1720.96 L991.39 1720.96 L991.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="991.39,1720.96 991.39,1720.96 991.672,1720.96 991.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M991.672 1720.76 L991.672 1720.96 L991.954 1720.96 L991.954 1720.76 L991.672 1720.76 L991.672 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="991.672,1720.76 991.672,1720.96 991.954,1720.96 991.954,1720.76 991.672,1720.76 "/>
<path clip-path="url(#clip322)" d="M991.954 1720.96 L991.954 1720.96 L992.235 1720.96 L992.235 1720.96 L991.954 1720.96 L991.954 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="991.954,1720.96 991.954,1720.96 992.235,1720.96 991.954,1720.96 "/>
<path clip-path="url(#clip322)" d="M992.235 1720.76 L992.235 1720.96 L992.517 1720.96 L992.517 1720.76 L992.235 1720.76 L992.235 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="992.235,1720.76 992.235,1720.96 992.517,1720.96 992.517,1720.76 992.235,1720.76 "/>
<path clip-path="url(#clip322)" d="M992.517 1720.37 L992.517 1720.96 L992.799 1720.96 L992.799 1720.37 L992.517 1720.37 L992.517 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="992.517,1720.37 992.517,1720.96 992.799,1720.96 992.799,1720.37 992.517,1720.37 "/>
<path clip-path="url(#clip322)" d="M992.799 1720.96 L992.799 1720.96 L993.081 1720.96 L993.081 1720.96 L992.799 1720.96 L992.799 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="992.799,1720.96 992.799,1720.96 993.081,1720.96 992.799,1720.96 "/>
<path clip-path="url(#clip322)" d="M993.081 1720.96 L993.081 1720.96 L993.362 1720.96 L993.362 1720.96 L993.081 1720.96 L993.081 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="993.081,1720.96 993.081,1720.96 993.362,1720.96 993.081,1720.96 "/>
<path clip-path="url(#clip322)" d="M993.362 1720.76 L993.362 1720.96 L993.644 1720.96 L993.644 1720.76 L993.362 1720.76 L993.362 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="993.362,1720.76 993.362,1720.96 993.644,1720.96 993.644,1720.76 993.362,1720.76 "/>
<path clip-path="url(#clip322)" d="M993.644 1720.76 L993.644 1720.96 L993.926 1720.96 L993.926 1720.76 L993.644 1720.76 L993.644 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="993.644,1720.76 993.644,1720.96 993.926,1720.96 993.926,1720.76 993.644,1720.76 "/>
<path clip-path="url(#clip322)" d="M993.926 1720.76 L993.926 1720.96 L994.207 1720.96 L994.207 1720.76 L993.926 1720.76 L993.926 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="993.926,1720.76 993.926,1720.96 994.207,1720.96 994.207,1720.76 993.926,1720.76 "/>
<path clip-path="url(#clip322)" d="M994.207 1720.96 L994.207 1720.96 L994.489 1720.96 L994.489 1720.96 L994.207 1720.96 L994.207 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="994.207,1720.96 994.207,1720.96 994.489,1720.96 994.207,1720.96 "/>
<path clip-path="url(#clip322)" d="M994.489 1720.37 L994.489 1720.96 L994.771 1720.96 L994.771 1720.37 L994.489 1720.37 L994.489 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="994.489,1720.37 994.489,1720.96 994.771,1720.96 994.771,1720.37 994.489,1720.37 "/>
<path clip-path="url(#clip322)" d="M994.771 1720.37 L994.771 1720.96 L995.053 1720.96 L995.053 1720.37 L994.771 1720.37 L994.771 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="994.771,1720.37 994.771,1720.96 995.053,1720.96 995.053,1720.37 994.771,1720.37 "/>
<path clip-path="url(#clip322)" d="M995.053 1720.56 L995.053 1720.96 L995.334 1720.96 L995.334 1720.56 L995.053 1720.56 L995.053 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="995.053,1720.56 995.053,1720.96 995.334,1720.96 995.334,1720.56 995.053,1720.56 "/>
<path clip-path="url(#clip322)" d="M995.334 1720.56 L995.334 1720.96 L995.616 1720.96 L995.616 1720.56 L995.334 1720.56 L995.334 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="995.334,1720.56 995.334,1720.96 995.616,1720.96 995.616,1720.56 995.334,1720.56 "/>
<path clip-path="url(#clip322)" d="M995.616 1720.56 L995.616 1720.96 L995.898 1720.96 L995.898 1720.56 L995.616 1720.56 L995.616 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="995.616,1720.56 995.616,1720.96 995.898,1720.96 995.898,1720.56 995.616,1720.56 "/>
<path clip-path="url(#clip322)" d="M995.898 1720.96 L995.898 1720.96 L996.18 1720.96 L996.18 1720.96 L995.898 1720.96 L995.898 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="995.898,1720.96 995.898,1720.96 996.18,1720.96 995.898,1720.96 "/>
<path clip-path="url(#clip322)" d="M996.18 1720.56 L996.18 1720.96 L996.461 1720.96 L996.461 1720.56 L996.18 1720.56 L996.18 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="996.18,1720.56 996.18,1720.96 996.461,1720.96 996.461,1720.56 996.18,1720.56 "/>
<path clip-path="url(#clip322)" d="M996.461 1720.96 L996.461 1720.96 L996.743 1720.96 L996.743 1720.96 L996.461 1720.96 L996.461 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="996.461,1720.96 996.461,1720.96 996.743,1720.96 996.461,1720.96 "/>
<path clip-path="url(#clip322)" d="M996.743 1720.96 L996.743 1720.96 L997.025 1720.96 L997.025 1720.96 L996.743 1720.96 L996.743 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="996.743,1720.96 996.743,1720.96 997.025,1720.96 996.743,1720.96 "/>
<path clip-path="url(#clip322)" d="M997.025 1720.96 L997.025 1720.96 L997.306 1720.96 L997.306 1720.96 L997.025 1720.96 L997.025 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="997.025,1720.96 997.025,1720.96 997.306,1720.96 997.025,1720.96 "/>
<path clip-path="url(#clip322)" d="M997.306 1720.76 L997.306 1720.96 L997.588 1720.96 L997.588 1720.76 L997.306 1720.76 L997.306 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="997.306,1720.76 997.306,1720.96 997.588,1720.96 997.588,1720.76 997.306,1720.76 "/>
<path clip-path="url(#clip322)" d="M997.588 1720.56 L997.588 1720.96 L997.87 1720.96 L997.87 1720.56 L997.588 1720.56 L997.588 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="997.588,1720.56 997.588,1720.96 997.87,1720.96 997.87,1720.56 997.588,1720.56 "/>
<path clip-path="url(#clip322)" d="M997.87 1720.96 L997.87 1720.96 L998.152 1720.96 L998.152 1720.96 L997.87 1720.96 L997.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="997.87,1720.96 997.87,1720.96 998.152,1720.96 997.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M998.152 1720.96 L998.152 1720.96 L998.433 1720.96 L998.433 1720.96 L998.152 1720.96 L998.152 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="998.152,1720.96 998.152,1720.96 998.433,1720.96 998.152,1720.96 "/>
<path clip-path="url(#clip322)" d="M998.433 1720.96 L998.433 1720.96 L998.715 1720.96 L998.715 1720.96 L998.433 1720.96 L998.433 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="998.433,1720.96 998.433,1720.96 998.715,1720.96 998.433,1720.96 "/>
<path clip-path="url(#clip322)" d="M998.715 1720.76 L998.715 1720.96 L998.997 1720.96 L998.997 1720.76 L998.715 1720.76 L998.715 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="998.715,1720.76 998.715,1720.96 998.997,1720.96 998.997,1720.76 998.715,1720.76 "/>
<path clip-path="url(#clip322)" d="M998.997 1720.96 L998.997 1720.96 L999.279 1720.96 L999.279 1720.96 L998.997 1720.96 L998.997 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="998.997,1720.96 998.997,1720.96 999.279,1720.96 998.997,1720.96 "/>
<path clip-path="url(#clip322)" d="M999.279 1720.96 L999.279 1720.96 L999.56 1720.96 L999.56 1720.96 L999.279 1720.96 L999.279 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="999.279,1720.96 999.279,1720.96 999.56,1720.96 999.279,1720.96 "/>
<path clip-path="url(#clip322)" d="M999.56 1720.76 L999.56 1720.96 L999.842 1720.96 L999.842 1720.76 L999.56 1720.76 L999.56 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="999.56,1720.76 999.56,1720.96 999.842,1720.96 999.842,1720.76 999.56,1720.76 "/>
<path clip-path="url(#clip322)" d="M999.842 1720.96 L999.842 1720.96 L1000.12 1720.96 L1000.12 1720.96 L999.842 1720.96 L999.842 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="999.842,1720.96 999.842,1720.96 1000.12,1720.96 999.842,1720.96 "/>
<path clip-path="url(#clip322)" d="M1000.12 1720.96 L1000.12 1720.96 L1000.41 1720.96 L1000.41 1720.96 L1000.12 1720.96 L1000.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1000.12,1720.96 1000.12,1720.96 1000.41,1720.96 1000.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1000.41 1720.96 L1000.41 1720.96 L1000.69 1720.96 L1000.69 1720.96 L1000.41 1720.96 L1000.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1000.41,1720.96 1000.41,1720.96 1000.69,1720.96 1000.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1000.69 1720.96 L1000.69 1720.96 L1000.97 1720.96 L1000.97 1720.96 L1000.69 1720.96 L1000.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1000.69,1720.96 1000.69,1720.96 1000.97,1720.96 1000.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1000.97 1720.96 L1000.97 1720.96 L1001.25 1720.96 L1001.25 1720.96 L1000.97 1720.96 L1000.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1000.97,1720.96 1000.97,1720.96 1001.25,1720.96 1000.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1001.25 1720.76 L1001.25 1720.96 L1001.53 1720.96 L1001.53 1720.76 L1001.25 1720.76 L1001.25 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1001.25,1720.76 1001.25,1720.96 1001.53,1720.96 1001.53,1720.76 1001.25,1720.76 "/>
<path clip-path="url(#clip322)" d="M1001.53 1720.76 L1001.53 1720.96 L1001.81 1720.96 L1001.81 1720.76 L1001.53 1720.76 L1001.53 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1001.53,1720.76 1001.53,1720.96 1001.81,1720.96 1001.81,1720.76 1001.53,1720.76 "/>
<path clip-path="url(#clip322)" d="M1001.81 1720.76 L1001.81 1720.96 L1002.1 1720.96 L1002.1 1720.76 L1001.81 1720.76 L1001.81 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1001.81,1720.76 1001.81,1720.96 1002.1,1720.96 1002.1,1720.76 1001.81,1720.76 "/>
<path clip-path="url(#clip322)" d="M1002.1 1720.96 L1002.1 1720.96 L1002.38 1720.96 L1002.38 1720.96 L1002.1 1720.96 L1002.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1002.1,1720.96 1002.1,1720.96 1002.38,1720.96 1002.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1002.38 1720.37 L1002.38 1720.96 L1002.66 1720.96 L1002.66 1720.37 L1002.38 1720.37 L1002.38 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1002.38,1720.37 1002.38,1720.96 1002.66,1720.96 1002.66,1720.37 1002.38,1720.37 "/>
<path clip-path="url(#clip322)" d="M1002.66 1720.96 L1002.66 1720.96 L1002.94 1720.96 L1002.94 1720.96 L1002.66 1720.96 L1002.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1002.66,1720.96 1002.66,1720.96 1002.94,1720.96 1002.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1002.94 1720.37 L1002.94 1720.96 L1003.22 1720.96 L1003.22 1720.37 L1002.94 1720.37 L1002.94 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1002.94,1720.37 1002.94,1720.96 1003.22,1720.96 1003.22,1720.37 1002.94,1720.37 "/>
<path clip-path="url(#clip322)" d="M1003.22 1720.76 L1003.22 1720.96 L1003.5 1720.96 L1003.5 1720.76 L1003.22 1720.76 L1003.22 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1003.22,1720.76 1003.22,1720.96 1003.5,1720.96 1003.5,1720.76 1003.22,1720.76 "/>
<path clip-path="url(#clip322)" d="M1003.5 1720.96 L1003.5 1720.96 L1003.79 1720.96 L1003.79 1720.96 L1003.5 1720.96 L1003.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1003.5,1720.96 1003.5,1720.96 1003.79,1720.96 1003.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1003.79 1720.76 L1003.79 1720.96 L1004.07 1720.96 L1004.07 1720.76 L1003.79 1720.76 L1003.79 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1003.79,1720.76 1003.79,1720.96 1004.07,1720.96 1004.07,1720.76 1003.79,1720.76 "/>
<path clip-path="url(#clip322)" d="M1004.07 1720.56 L1004.07 1720.96 L1004.35 1720.96 L1004.35 1720.56 L1004.07 1720.56 L1004.07 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1004.07,1720.56 1004.07,1720.96 1004.35,1720.96 1004.35,1720.56 1004.07,1720.56 "/>
<path clip-path="url(#clip322)" d="M1004.35 1720.96 L1004.35 1720.96 L1004.63 1720.96 L1004.63 1720.96 L1004.35 1720.96 L1004.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1004.35,1720.96 1004.35,1720.96 1004.63,1720.96 1004.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1004.63 1720.96 L1004.63 1720.96 L1004.91 1720.96 L1004.91 1720.96 L1004.63 1720.96 L1004.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1004.63,1720.96 1004.63,1720.96 1004.91,1720.96 1004.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1004.91 1720.96 L1004.91 1720.96 L1005.19 1720.96 L1005.19 1720.96 L1004.91 1720.96 L1004.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1004.91,1720.96 1004.91,1720.96 1005.19,1720.96 1004.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1005.19 1720.76 L1005.19 1720.96 L1005.48 1720.96 L1005.48 1720.76 L1005.19 1720.76 L1005.19 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1005.19,1720.76 1005.19,1720.96 1005.48,1720.96 1005.48,1720.76 1005.19,1720.76 "/>
<path clip-path="url(#clip322)" d="M1005.48 1720.76 L1005.48 1720.96 L1005.76 1720.96 L1005.76 1720.76 L1005.48 1720.76 L1005.48 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1005.48,1720.76 1005.48,1720.96 1005.76,1720.96 1005.76,1720.76 1005.48,1720.76 "/>
<path clip-path="url(#clip322)" d="M1005.76 1720.56 L1005.76 1720.96 L1006.04 1720.96 L1006.04 1720.56 L1005.76 1720.56 L1005.76 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1005.76,1720.56 1005.76,1720.96 1006.04,1720.96 1006.04,1720.56 1005.76,1720.56 "/>
<path clip-path="url(#clip322)" d="M1006.04 1720.96 L1006.04 1720.96 L1006.32 1720.96 L1006.32 1720.96 L1006.04 1720.96 L1006.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1006.04,1720.96 1006.04,1720.96 1006.32,1720.96 1006.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1006.32 1720.76 L1006.32 1720.96 L1006.6 1720.96 L1006.6 1720.76 L1006.32 1720.76 L1006.32 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1006.32,1720.76 1006.32,1720.96 1006.6,1720.96 1006.6,1720.76 1006.32,1720.76 "/>
<path clip-path="url(#clip322)" d="M1006.6 1720.96 L1006.6 1720.96 L1006.89 1720.96 L1006.89 1720.96 L1006.6 1720.96 L1006.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1006.6,1720.96 1006.6,1720.96 1006.89,1720.96 1006.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1006.89 1720.76 L1006.89 1720.96 L1007.17 1720.96 L1007.17 1720.76 L1006.89 1720.76 L1006.89 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1006.89,1720.76 1006.89,1720.96 1007.17,1720.96 1007.17,1720.76 1006.89,1720.76 "/>
<path clip-path="url(#clip322)" d="M1007.17 1720.96 L1007.17 1720.96 L1007.45 1720.96 L1007.45 1720.96 L1007.17 1720.96 L1007.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1007.17,1720.96 1007.17,1720.96 1007.45,1720.96 1007.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1007.45 1720.96 L1007.45 1720.96 L1007.73 1720.96 L1007.73 1720.96 L1007.45 1720.96 L1007.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1007.45,1720.96 1007.45,1720.96 1007.73,1720.96 1007.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1007.73 1720.96 L1007.73 1720.96 L1008.01 1720.96 L1008.01 1720.96 L1007.73 1720.96 L1007.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1007.73,1720.96 1007.73,1720.96 1008.01,1720.96 1007.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1008.01 1720.96 L1008.01 1720.96 L1008.29 1720.96 L1008.29 1720.96 L1008.01 1720.96 L1008.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1008.01,1720.96 1008.01,1720.96 1008.29,1720.96 1008.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1008.29 1720.56 L1008.29 1720.96 L1008.58 1720.96 L1008.58 1720.56 L1008.29 1720.56 L1008.29 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1008.29,1720.56 1008.29,1720.96 1008.58,1720.96 1008.58,1720.56 1008.29,1720.56 "/>
<path clip-path="url(#clip322)" d="M1008.58 1720.76 L1008.58 1720.96 L1008.86 1720.96 L1008.86 1720.76 L1008.58 1720.76 L1008.58 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1008.58,1720.76 1008.58,1720.96 1008.86,1720.96 1008.86,1720.76 1008.58,1720.76 "/>
<path clip-path="url(#clip322)" d="M1008.86 1720.96 L1008.86 1720.96 L1009.14 1720.96 L1009.14 1720.96 L1008.86 1720.96 L1008.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1008.86,1720.96 1008.86,1720.96 1009.14,1720.96 1008.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1009.14 1720.96 L1009.14 1720.96 L1009.42 1720.96 L1009.42 1720.96 L1009.14 1720.96 L1009.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1009.14,1720.96 1009.14,1720.96 1009.42,1720.96 1009.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1009.42 1720.76 L1009.42 1720.96 L1009.7 1720.96 L1009.7 1720.76 L1009.42 1720.76 L1009.42 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1009.42,1720.76 1009.42,1720.96 1009.7,1720.96 1009.7,1720.76 1009.42,1720.76 "/>
<path clip-path="url(#clip322)" d="M1009.7 1720.96 L1009.7 1720.96 L1009.98 1720.96 L1009.98 1720.96 L1009.7 1720.96 L1009.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1009.7,1720.96 1009.7,1720.96 1009.98,1720.96 1009.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1009.98 1720.56 L1009.98 1720.96 L1010.27 1720.96 L1010.27 1720.56 L1009.98 1720.56 L1009.98 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1009.98,1720.56 1009.98,1720.96 1010.27,1720.96 1010.27,1720.56 1009.98,1720.56 "/>
<path clip-path="url(#clip322)" d="M1010.27 1720.56 L1010.27 1720.96 L1010.55 1720.96 L1010.55 1720.56 L1010.27 1720.56 L1010.27 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1010.27,1720.56 1010.27,1720.96 1010.55,1720.96 1010.55,1720.56 1010.27,1720.56 "/>
<path clip-path="url(#clip322)" d="M1010.55 1720.37 L1010.55 1720.96 L1010.83 1720.96 L1010.83 1720.37 L1010.55 1720.37 L1010.55 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1010.55,1720.37 1010.55,1720.96 1010.83,1720.96 1010.83,1720.37 1010.55,1720.37 "/>
<path clip-path="url(#clip322)" d="M1010.83 1720.96 L1010.83 1720.96 L1011.11 1720.96 L1011.11 1720.96 L1010.83 1720.96 L1010.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1010.83,1720.96 1010.83,1720.96 1011.11,1720.96 1010.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1011.11 1720.56 L1011.11 1720.96 L1011.39 1720.96 L1011.39 1720.56 L1011.11 1720.56 L1011.11 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1011.11,1720.56 1011.11,1720.96 1011.39,1720.96 1011.39,1720.56 1011.11,1720.56 "/>
<path clip-path="url(#clip322)" d="M1011.39 1720.76 L1011.39 1720.96 L1011.67 1720.96 L1011.67 1720.76 L1011.39 1720.76 L1011.39 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1011.39,1720.76 1011.39,1720.96 1011.67,1720.96 1011.67,1720.76 1011.39,1720.76 "/>
<path clip-path="url(#clip322)" d="M1011.67 1720.76 L1011.67 1720.96 L1011.96 1720.96 L1011.96 1720.76 L1011.67 1720.76 L1011.67 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1011.67,1720.76 1011.67,1720.96 1011.96,1720.96 1011.96,1720.76 1011.67,1720.76 "/>
<path clip-path="url(#clip322)" d="M1011.96 1720.76 L1011.96 1720.96 L1012.24 1720.96 L1012.24 1720.76 L1011.96 1720.76 L1011.96 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1011.96,1720.76 1011.96,1720.96 1012.24,1720.96 1012.24,1720.76 1011.96,1720.76 "/>
<path clip-path="url(#clip322)" d="M1012.24 1720.76 L1012.24 1720.96 L1012.52 1720.96 L1012.52 1720.76 L1012.24 1720.76 L1012.24 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1012.24,1720.76 1012.24,1720.96 1012.52,1720.96 1012.52,1720.76 1012.24,1720.76 "/>
<path clip-path="url(#clip322)" d="M1012.52 1720.96 L1012.52 1720.96 L1012.8 1720.96 L1012.8 1720.96 L1012.52 1720.96 L1012.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1012.52,1720.96 1012.52,1720.96 1012.8,1720.96 1012.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1012.8 1720.56 L1012.8 1720.96 L1013.08 1720.96 L1013.08 1720.56 L1012.8 1720.56 L1012.8 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1012.8,1720.56 1012.8,1720.96 1013.08,1720.96 1013.08,1720.56 1012.8,1720.56 "/>
<path clip-path="url(#clip322)" d="M1013.08 1720.96 L1013.08 1720.96 L1013.36 1720.96 L1013.36 1720.96 L1013.08 1720.96 L1013.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1013.08,1720.96 1013.08,1720.96 1013.36,1720.96 1013.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1013.36 1720.96 L1013.36 1720.96 L1013.65 1720.96 L1013.65 1720.96 L1013.36 1720.96 L1013.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1013.36,1720.96 1013.36,1720.96 1013.65,1720.96 1013.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1013.65 1720.96 L1013.65 1720.96 L1013.93 1720.96 L1013.93 1720.96 L1013.65 1720.96 L1013.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1013.65,1720.96 1013.65,1720.96 1013.93,1720.96 1013.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1013.93 1720.96 L1013.93 1720.96 L1014.21 1720.96 L1014.21 1720.96 L1013.93 1720.96 L1013.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1013.93,1720.96 1013.93,1720.96 1014.21,1720.96 1013.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1014.21 1720.76 L1014.21 1720.96 L1014.49 1720.96 L1014.49 1720.76 L1014.21 1720.76 L1014.21 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1014.21,1720.76 1014.21,1720.96 1014.49,1720.96 1014.49,1720.76 1014.21,1720.76 "/>
<path clip-path="url(#clip322)" d="M1014.49 1720.96 L1014.49 1720.96 L1014.77 1720.96 L1014.77 1720.96 L1014.49 1720.96 L1014.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1014.49,1720.96 1014.49,1720.96 1014.77,1720.96 1014.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1014.77 1720.76 L1014.77 1720.96 L1015.06 1720.96 L1015.06 1720.76 L1014.77 1720.76 L1014.77 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1014.77,1720.76 1014.77,1720.96 1015.06,1720.96 1015.06,1720.76 1014.77,1720.76 "/>
<path clip-path="url(#clip322)" d="M1015.06 1720.56 L1015.06 1720.96 L1015.34 1720.96 L1015.34 1720.56 L1015.06 1720.56 L1015.06 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1015.06,1720.56 1015.06,1720.96 1015.34,1720.96 1015.34,1720.56 1015.06,1720.56 "/>
<path clip-path="url(#clip322)" d="M1015.34 1720.37 L1015.34 1720.96 L1015.62 1720.96 L1015.62 1720.37 L1015.34 1720.37 L1015.34 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1015.34,1720.37 1015.34,1720.96 1015.62,1720.96 1015.62,1720.37 1015.34,1720.37 "/>
<path clip-path="url(#clip322)" d="M1015.62 1720.96 L1015.62 1720.96 L1015.9 1720.96 L1015.9 1720.96 L1015.62 1720.96 L1015.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1015.62,1720.96 1015.62,1720.96 1015.9,1720.96 1015.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1015.9 1720.96 L1015.9 1720.96 L1016.18 1720.96 L1016.18 1720.96 L1015.9 1720.96 L1015.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1015.9,1720.96 1015.9,1720.96 1016.18,1720.96 1015.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1016.18 1720.96 L1016.18 1720.96 L1016.46 1720.96 L1016.46 1720.96 L1016.18 1720.96 L1016.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1016.18,1720.96 1016.18,1720.96 1016.46,1720.96 1016.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1016.46 1720.96 L1016.46 1720.96 L1016.75 1720.96 L1016.75 1720.96 L1016.46 1720.96 L1016.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1016.46,1720.96 1016.46,1720.96 1016.75,1720.96 1016.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1016.75 1720.56 L1016.75 1720.96 L1017.03 1720.96 L1017.03 1720.56 L1016.75 1720.56 L1016.75 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1016.75,1720.56 1016.75,1720.96 1017.03,1720.96 1017.03,1720.56 1016.75,1720.56 "/>
<path clip-path="url(#clip322)" d="M1017.03 1720.96 L1017.03 1720.96 L1017.31 1720.96 L1017.31 1720.96 L1017.03 1720.96 L1017.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1017.03,1720.96 1017.03,1720.96 1017.31,1720.96 1017.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1017.31 1720.96 L1017.31 1720.96 L1017.59 1720.96 L1017.59 1720.96 L1017.31 1720.96 L1017.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1017.31,1720.96 1017.31,1720.96 1017.59,1720.96 1017.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1017.59 1720.37 L1017.59 1720.96 L1017.87 1720.96 L1017.87 1720.37 L1017.59 1720.37 L1017.59 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1017.59,1720.37 1017.59,1720.96 1017.87,1720.96 1017.87,1720.37 1017.59,1720.37 "/>
<path clip-path="url(#clip322)" d="M1017.87 1720.96 L1017.87 1720.96 L1018.15 1720.96 L1018.15 1720.96 L1017.87 1720.96 L1017.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1017.87,1720.96 1017.87,1720.96 1018.15,1720.96 1017.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1018.15 1720.96 L1018.15 1720.96 L1018.44 1720.96 L1018.44 1720.96 L1018.15 1720.96 L1018.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1018.15,1720.96 1018.15,1720.96 1018.44,1720.96 1018.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1018.44 1720.76 L1018.44 1720.96 L1018.72 1720.96 L1018.72 1720.76 L1018.44 1720.76 L1018.44 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1018.44,1720.76 1018.44,1720.96 1018.72,1720.96 1018.72,1720.76 1018.44,1720.76 "/>
<path clip-path="url(#clip322)" d="M1018.72 1720.96 L1018.72 1720.96 L1019 1720.96 L1019 1720.96 L1018.72 1720.96 L1018.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1018.72,1720.96 1018.72,1720.96 1019,1720.96 1018.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1019 1720.56 L1019 1720.96 L1019.28 1720.96 L1019.28 1720.56 L1019 1720.56 L1019 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1019,1720.56 1019,1720.96 1019.28,1720.96 1019.28,1720.56 1019,1720.56 "/>
<path clip-path="url(#clip322)" d="M1019.28 1720.76 L1019.28 1720.96 L1019.56 1720.96 L1019.56 1720.76 L1019.28 1720.76 L1019.28 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1019.28,1720.76 1019.28,1720.96 1019.56,1720.96 1019.56,1720.76 1019.28,1720.76 "/>
<path clip-path="url(#clip322)" d="M1019.56 1720.96 L1019.56 1720.96 L1019.84 1720.96 L1019.84 1720.96 L1019.56 1720.96 L1019.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1019.56,1720.96 1019.56,1720.96 1019.84,1720.96 1019.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1019.84 1720.96 L1019.84 1720.96 L1020.13 1720.96 L1020.13 1720.96 L1019.84 1720.96 L1019.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1019.84,1720.96 1019.84,1720.96 1020.13,1720.96 1019.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1020.13 1720.96 L1020.13 1720.96 L1020.41 1720.96 L1020.41 1720.96 L1020.13 1720.96 L1020.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1020.13,1720.96 1020.13,1720.96 1020.41,1720.96 1020.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1020.41 1720.76 L1020.41 1720.96 L1020.69 1720.96 L1020.69 1720.76 L1020.41 1720.76 L1020.41 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1020.41,1720.76 1020.41,1720.96 1020.69,1720.96 1020.69,1720.76 1020.41,1720.76 "/>
<path clip-path="url(#clip322)" d="M1020.69 1720.76 L1020.69 1720.96 L1020.97 1720.96 L1020.97 1720.76 L1020.69 1720.76 L1020.69 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1020.69,1720.76 1020.69,1720.96 1020.97,1720.96 1020.97,1720.76 1020.69,1720.76 "/>
<path clip-path="url(#clip322)" d="M1020.97 1720.76 L1020.97 1720.96 L1021.25 1720.96 L1021.25 1720.76 L1020.97 1720.76 L1020.97 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1020.97,1720.76 1020.97,1720.96 1021.25,1720.96 1021.25,1720.76 1020.97,1720.76 "/>
<path clip-path="url(#clip322)" d="M1021.25 1720.76 L1021.25 1720.96 L1021.53 1720.96 L1021.53 1720.76 L1021.25 1720.76 L1021.25 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1021.25,1720.76 1021.25,1720.96 1021.53,1720.96 1021.53,1720.76 1021.25,1720.76 "/>
<path clip-path="url(#clip322)" d="M1021.53 1720.37 L1021.53 1720.96 L1021.82 1720.96 L1021.82 1720.37 L1021.53 1720.37 L1021.53 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1021.53,1720.37 1021.53,1720.96 1021.82,1720.96 1021.82,1720.37 1021.53,1720.37 "/>
<path clip-path="url(#clip322)" d="M1021.82 1720.96 L1021.82 1720.96 L1022.1 1720.96 L1022.1 1720.96 L1021.82 1720.96 L1021.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1021.82,1720.96 1021.82,1720.96 1022.1,1720.96 1021.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1022.1 1720.76 L1022.1 1720.96 L1022.38 1720.96 L1022.38 1720.76 L1022.1 1720.76 L1022.1 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1022.1,1720.76 1022.1,1720.96 1022.38,1720.96 1022.38,1720.76 1022.1,1720.76 "/>
<path clip-path="url(#clip322)" d="M1022.38 1720.56 L1022.38 1720.96 L1022.66 1720.96 L1022.66 1720.56 L1022.38 1720.56 L1022.38 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1022.38,1720.56 1022.38,1720.96 1022.66,1720.96 1022.66,1720.56 1022.38,1720.56 "/>
<path clip-path="url(#clip322)" d="M1022.66 1720.96 L1022.66 1720.96 L1022.94 1720.96 L1022.94 1720.96 L1022.66 1720.96 L1022.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1022.66,1720.96 1022.66,1720.96 1022.94,1720.96 1022.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1022.94 1720.96 L1022.94 1720.96 L1023.23 1720.96 L1023.23 1720.96 L1022.94 1720.96 L1022.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1022.94,1720.96 1022.94,1720.96 1023.23,1720.96 1022.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1023.23 1720.76 L1023.23 1720.96 L1023.51 1720.96 L1023.51 1720.76 L1023.23 1720.76 L1023.23 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1023.23,1720.76 1023.23,1720.96 1023.51,1720.96 1023.51,1720.76 1023.23,1720.76 "/>
<path clip-path="url(#clip322)" d="M1023.51 1720.76 L1023.51 1720.96 L1023.79 1720.96 L1023.79 1720.76 L1023.51 1720.76 L1023.51 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1023.51,1720.76 1023.51,1720.96 1023.79,1720.96 1023.79,1720.76 1023.51,1720.76 "/>
<path clip-path="url(#clip322)" d="M1023.79 1720.76 L1023.79 1720.96 L1024.07 1720.96 L1024.07 1720.76 L1023.79 1720.76 L1023.79 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1023.79,1720.76 1023.79,1720.96 1024.07,1720.96 1024.07,1720.76 1023.79,1720.76 "/>
<path clip-path="url(#clip322)" d="M1024.07 1720.56 L1024.07 1720.96 L1024.35 1720.96 L1024.35 1720.56 L1024.07 1720.56 L1024.07 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1024.07,1720.56 1024.07,1720.96 1024.35,1720.96 1024.35,1720.56 1024.07,1720.56 "/>
<path clip-path="url(#clip322)" d="M1024.35 1720.96 L1024.35 1720.96 L1024.63 1720.96 L1024.63 1720.96 L1024.35 1720.96 L1024.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1024.35,1720.96 1024.35,1720.96 1024.63,1720.96 1024.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1024.63 1720.96 L1024.63 1720.96 L1024.92 1720.96 L1024.92 1720.96 L1024.63 1720.96 L1024.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1024.63,1720.96 1024.63,1720.96 1024.92,1720.96 1024.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1024.92 1720.96 L1024.92 1720.96 L1025.2 1720.96 L1025.2 1720.96 L1024.92 1720.96 L1024.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1024.92,1720.96 1024.92,1720.96 1025.2,1720.96 1024.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1025.2 1720.96 L1025.2 1720.96 L1025.48 1720.96 L1025.48 1720.96 L1025.2 1720.96 L1025.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1025.2,1720.96 1025.2,1720.96 1025.48,1720.96 1025.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1025.48 1720.76 L1025.48 1720.96 L1025.76 1720.96 L1025.76 1720.76 L1025.48 1720.76 L1025.48 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1025.48,1720.76 1025.48,1720.96 1025.76,1720.96 1025.76,1720.76 1025.48,1720.76 "/>
<path clip-path="url(#clip322)" d="M1025.76 1720.96 L1025.76 1720.96 L1026.04 1720.96 L1026.04 1720.96 L1025.76 1720.96 L1025.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1025.76,1720.96 1025.76,1720.96 1026.04,1720.96 1025.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1026.04 1720.96 L1026.04 1720.96 L1026.32 1720.96 L1026.32 1720.96 L1026.04 1720.96 L1026.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1026.04,1720.96 1026.04,1720.96 1026.32,1720.96 1026.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1026.32 1720.96 L1026.32 1720.96 L1026.61 1720.96 L1026.61 1720.96 L1026.32 1720.96 L1026.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1026.32,1720.96 1026.32,1720.96 1026.61,1720.96 1026.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1026.61 1720.76 L1026.61 1720.96 L1026.89 1720.96 L1026.89 1720.76 L1026.61 1720.76 L1026.61 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1026.61,1720.76 1026.61,1720.96 1026.89,1720.96 1026.89,1720.76 1026.61,1720.76 "/>
<path clip-path="url(#clip322)" d="M1026.89 1720.56 L1026.89 1720.96 L1027.17 1720.96 L1027.17 1720.56 L1026.89 1720.56 L1026.89 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1026.89,1720.56 1026.89,1720.96 1027.17,1720.96 1027.17,1720.56 1026.89,1720.56 "/>
<path clip-path="url(#clip322)" d="M1027.17 1720.96 L1027.17 1720.96 L1027.45 1720.96 L1027.45 1720.96 L1027.17 1720.96 L1027.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1027.17,1720.96 1027.17,1720.96 1027.45,1720.96 1027.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1027.45 1720.76 L1027.45 1720.96 L1027.73 1720.96 L1027.73 1720.76 L1027.45 1720.76 L1027.45 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1027.45,1720.76 1027.45,1720.96 1027.73,1720.96 1027.73,1720.76 1027.45,1720.76 "/>
<path clip-path="url(#clip322)" d="M1027.73 1720.56 L1027.73 1720.96 L1028.01 1720.96 L1028.01 1720.56 L1027.73 1720.56 L1027.73 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1027.73,1720.56 1027.73,1720.96 1028.01,1720.96 1028.01,1720.56 1027.73,1720.56 "/>
<path clip-path="url(#clip322)" d="M1028.01 1720.76 L1028.01 1720.96 L1028.3 1720.96 L1028.3 1720.76 L1028.01 1720.76 L1028.01 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1028.01,1720.76 1028.01,1720.96 1028.3,1720.96 1028.3,1720.76 1028.01,1720.76 "/>
<path clip-path="url(#clip322)" d="M1028.3 1720.76 L1028.3 1720.96 L1028.58 1720.96 L1028.58 1720.76 L1028.3 1720.76 L1028.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1028.3,1720.76 1028.3,1720.96 1028.58,1720.96 1028.58,1720.76 1028.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1028.58 1720.76 L1028.58 1720.96 L1028.86 1720.96 L1028.86 1720.76 L1028.58 1720.76 L1028.58 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1028.58,1720.76 1028.58,1720.96 1028.86,1720.96 1028.86,1720.76 1028.58,1720.76 "/>
<path clip-path="url(#clip322)" d="M1028.86 1720.56 L1028.86 1720.96 L1029.14 1720.96 L1029.14 1720.56 L1028.86 1720.56 L1028.86 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1028.86,1720.56 1028.86,1720.96 1029.14,1720.96 1029.14,1720.56 1028.86,1720.56 "/>
<path clip-path="url(#clip322)" d="M1029.14 1720.96 L1029.14 1720.96 L1029.42 1720.96 L1029.42 1720.96 L1029.14 1720.96 L1029.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1029.14,1720.96 1029.14,1720.96 1029.42,1720.96 1029.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1029.42 1720.56 L1029.42 1720.96 L1029.7 1720.96 L1029.7 1720.56 L1029.42 1720.56 L1029.42 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1029.42,1720.56 1029.42,1720.96 1029.7,1720.96 1029.7,1720.56 1029.42,1720.56 "/>
<path clip-path="url(#clip322)" d="M1029.7 1720.56 L1029.7 1720.96 L1029.99 1720.96 L1029.99 1720.56 L1029.7 1720.56 L1029.7 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1029.7,1720.56 1029.7,1720.96 1029.99,1720.96 1029.99,1720.56 1029.7,1720.56 "/>
<path clip-path="url(#clip322)" d="M1029.99 1720.96 L1029.99 1720.96 L1030.27 1720.96 L1030.27 1720.96 L1029.99 1720.96 L1029.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1029.99,1720.96 1029.99,1720.96 1030.27,1720.96 1029.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1030.27 1720.76 L1030.27 1720.96 L1030.55 1720.96 L1030.55 1720.76 L1030.27 1720.76 L1030.27 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1030.27,1720.76 1030.27,1720.96 1030.55,1720.96 1030.55,1720.76 1030.27,1720.76 "/>
<path clip-path="url(#clip322)" d="M1030.55 1720.96 L1030.55 1720.96 L1030.83 1720.96 L1030.83 1720.96 L1030.55 1720.96 L1030.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1030.55,1720.96 1030.55,1720.96 1030.83,1720.96 1030.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1030.83 1720.96 L1030.83 1720.96 L1031.11 1720.96 L1031.11 1720.96 L1030.83 1720.96 L1030.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1030.83,1720.96 1030.83,1720.96 1031.11,1720.96 1030.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1031.11 1720.76 L1031.11 1720.96 L1031.4 1720.96 L1031.4 1720.76 L1031.11 1720.76 L1031.11 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1031.11,1720.76 1031.11,1720.96 1031.4,1720.96 1031.4,1720.76 1031.11,1720.76 "/>
<path clip-path="url(#clip322)" d="M1031.4 1720.76 L1031.4 1720.96 L1031.68 1720.96 L1031.68 1720.76 L1031.4 1720.76 L1031.4 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1031.4,1720.76 1031.4,1720.96 1031.68,1720.96 1031.68,1720.76 1031.4,1720.76 "/>
<path clip-path="url(#clip322)" d="M1031.68 1720.56 L1031.68 1720.96 L1031.96 1720.96 L1031.96 1720.56 L1031.68 1720.56 L1031.68 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1031.68,1720.56 1031.68,1720.96 1031.96,1720.96 1031.96,1720.56 1031.68,1720.56 "/>
<path clip-path="url(#clip322)" d="M1031.96 1720.76 L1031.96 1720.96 L1032.24 1720.96 L1032.24 1720.76 L1031.96 1720.76 L1031.96 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1031.96,1720.76 1031.96,1720.96 1032.24,1720.96 1032.24,1720.76 1031.96,1720.76 "/>
<path clip-path="url(#clip322)" d="M1032.24 1720.76 L1032.24 1720.96 L1032.52 1720.96 L1032.52 1720.76 L1032.24 1720.76 L1032.24 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1032.24,1720.76 1032.24,1720.96 1032.52,1720.96 1032.52,1720.76 1032.24,1720.76 "/>
<path clip-path="url(#clip322)" d="M1032.52 1720.76 L1032.52 1720.96 L1032.8 1720.96 L1032.8 1720.76 L1032.52 1720.76 L1032.52 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1032.52,1720.76 1032.52,1720.96 1032.8,1720.96 1032.8,1720.76 1032.52,1720.76 "/>
<path clip-path="url(#clip322)" d="M1032.8 1720.76 L1032.8 1720.96 L1033.09 1720.96 L1033.09 1720.76 L1032.8 1720.76 L1032.8 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1032.8,1720.76 1032.8,1720.96 1033.09,1720.96 1033.09,1720.76 1032.8,1720.76 "/>
<path clip-path="url(#clip322)" d="M1033.09 1720.76 L1033.09 1720.96 L1033.37 1720.96 L1033.37 1720.76 L1033.09 1720.76 L1033.09 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1033.09,1720.76 1033.09,1720.96 1033.37,1720.96 1033.37,1720.76 1033.09,1720.76 "/>
<path clip-path="url(#clip322)" d="M1033.37 1720.76 L1033.37 1720.96 L1033.65 1720.96 L1033.65 1720.76 L1033.37 1720.76 L1033.37 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1033.37,1720.76 1033.37,1720.96 1033.65,1720.96 1033.65,1720.76 1033.37,1720.76 "/>
<path clip-path="url(#clip322)" d="M1033.65 1720.96 L1033.65 1720.96 L1033.93 1720.96 L1033.93 1720.96 L1033.65 1720.96 L1033.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1033.65,1720.96 1033.65,1720.96 1033.93,1720.96 1033.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1033.93 1720.76 L1033.93 1720.96 L1034.21 1720.96 L1034.21 1720.76 L1033.93 1720.76 L1033.93 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1033.93,1720.76 1033.93,1720.96 1034.21,1720.96 1034.21,1720.76 1033.93,1720.76 "/>
<path clip-path="url(#clip322)" d="M1034.21 1720.96 L1034.21 1720.96 L1034.49 1720.96 L1034.49 1720.96 L1034.21 1720.96 L1034.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1034.21,1720.96 1034.21,1720.96 1034.49,1720.96 1034.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1034.49 1720.76 L1034.49 1720.96 L1034.78 1720.96 L1034.78 1720.76 L1034.49 1720.76 L1034.49 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1034.49,1720.76 1034.49,1720.96 1034.78,1720.96 1034.78,1720.76 1034.49,1720.76 "/>
<path clip-path="url(#clip322)" d="M1034.78 1720.37 L1034.78 1720.96 L1035.06 1720.96 L1035.06 1720.37 L1034.78 1720.37 L1034.78 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1034.78,1720.37 1034.78,1720.96 1035.06,1720.96 1035.06,1720.37 1034.78,1720.37 "/>
<path clip-path="url(#clip322)" d="M1035.06 1720.96 L1035.06 1720.96 L1035.34 1720.96 L1035.34 1720.96 L1035.06 1720.96 L1035.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1035.06,1720.96 1035.06,1720.96 1035.34,1720.96 1035.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1035.34 1720.76 L1035.34 1720.96 L1035.62 1720.96 L1035.62 1720.76 L1035.34 1720.76 L1035.34 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1035.34,1720.76 1035.34,1720.96 1035.62,1720.96 1035.62,1720.76 1035.34,1720.76 "/>
<path clip-path="url(#clip322)" d="M1035.62 1720.76 L1035.62 1720.96 L1035.9 1720.96 L1035.9 1720.76 L1035.62 1720.76 L1035.62 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1035.62,1720.76 1035.62,1720.96 1035.9,1720.96 1035.9,1720.76 1035.62,1720.76 "/>
<path clip-path="url(#clip322)" d="M1035.9 1720.76 L1035.9 1720.96 L1036.18 1720.96 L1036.18 1720.76 L1035.9 1720.76 L1035.9 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1035.9,1720.76 1035.9,1720.96 1036.18,1720.96 1036.18,1720.76 1035.9,1720.76 "/>
<path clip-path="url(#clip322)" d="M1036.18 1720.96 L1036.18 1720.96 L1036.47 1720.96 L1036.47 1720.96 L1036.18 1720.96 L1036.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1036.18,1720.96 1036.18,1720.96 1036.47,1720.96 1036.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1036.47 1720.96 L1036.47 1720.96 L1036.75 1720.96 L1036.75 1720.96 L1036.47 1720.96 L1036.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1036.47,1720.96 1036.47,1720.96 1036.75,1720.96 1036.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1036.75 1720.96 L1036.75 1720.96 L1037.03 1720.96 L1037.03 1720.96 L1036.75 1720.96 L1036.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1036.75,1720.96 1036.75,1720.96 1037.03,1720.96 1036.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1037.03 1720.96 L1037.03 1720.96 L1037.31 1720.96 L1037.31 1720.96 L1037.03 1720.96 L1037.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1037.03,1720.96 1037.03,1720.96 1037.31,1720.96 1037.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1037.31 1720.96 L1037.31 1720.96 L1037.59 1720.96 L1037.59 1720.96 L1037.31 1720.96 L1037.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1037.31,1720.96 1037.31,1720.96 1037.59,1720.96 1037.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1037.59 1720.96 L1037.59 1720.96 L1037.87 1720.96 L1037.87 1720.96 L1037.59 1720.96 L1037.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1037.59,1720.96 1037.59,1720.96 1037.87,1720.96 1037.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1037.87 1720.76 L1037.87 1720.96 L1038.16 1720.96 L1038.16 1720.76 L1037.87 1720.76 L1037.87 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1037.87,1720.76 1037.87,1720.96 1038.16,1720.96 1038.16,1720.76 1037.87,1720.76 "/>
<path clip-path="url(#clip322)" d="M1038.16 1720.76 L1038.16 1720.96 L1038.44 1720.96 L1038.44 1720.76 L1038.16 1720.76 L1038.16 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1038.16,1720.76 1038.16,1720.96 1038.44,1720.96 1038.44,1720.76 1038.16,1720.76 "/>
<path clip-path="url(#clip322)" d="M1038.44 1720.96 L1038.44 1720.96 L1038.72 1720.96 L1038.72 1720.96 L1038.44 1720.96 L1038.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1038.44,1720.96 1038.44,1720.96 1038.72,1720.96 1038.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1038.72 1720.76 L1038.72 1720.96 L1039 1720.96 L1039 1720.76 L1038.72 1720.76 L1038.72 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1038.72,1720.76 1038.72,1720.96 1039,1720.96 1039,1720.76 1038.72,1720.76 "/>
<path clip-path="url(#clip322)" d="M1039 1720.96 L1039 1720.96 L1039.28 1720.96 L1039.28 1720.96 L1039 1720.96 L1039 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1039,1720.96 1039,1720.96 1039.28,1720.96 1039,1720.96 "/>
<path clip-path="url(#clip322)" d="M1039.28 1720.96 L1039.28 1720.96 L1039.57 1720.96 L1039.57 1720.96 L1039.28 1720.96 L1039.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1039.28,1720.96 1039.28,1720.96 1039.57,1720.96 1039.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1039.57 1720.96 L1039.57 1720.96 L1039.85 1720.96 L1039.85 1720.96 L1039.57 1720.96 L1039.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1039.57,1720.96 1039.57,1720.96 1039.85,1720.96 1039.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1039.85 1720.76 L1039.85 1720.96 L1040.13 1720.96 L1040.13 1720.76 L1039.85 1720.76 L1039.85 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1039.85,1720.76 1039.85,1720.96 1040.13,1720.96 1040.13,1720.76 1039.85,1720.76 "/>
<path clip-path="url(#clip322)" d="M1040.13 1720.96 L1040.13 1720.96 L1040.41 1720.96 L1040.41 1720.96 L1040.13 1720.96 L1040.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1040.13,1720.96 1040.13,1720.96 1040.41,1720.96 1040.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1040.41 1720.96 L1040.41 1720.96 L1040.69 1720.96 L1040.69 1720.96 L1040.41 1720.96 L1040.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1040.41,1720.96 1040.41,1720.96 1040.69,1720.96 1040.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1040.69 1720.96 L1040.69 1720.96 L1040.97 1720.96 L1040.97 1720.96 L1040.69 1720.96 L1040.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1040.69,1720.96 1040.69,1720.96 1040.97,1720.96 1040.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1040.97 1720.56 L1040.97 1720.96 L1041.26 1720.96 L1041.26 1720.56 L1040.97 1720.56 L1040.97 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1040.97,1720.56 1040.97,1720.96 1041.26,1720.96 1041.26,1720.56 1040.97,1720.56 "/>
<path clip-path="url(#clip322)" d="M1041.26 1720.76 L1041.26 1720.96 L1041.54 1720.96 L1041.54 1720.76 L1041.26 1720.76 L1041.26 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1041.26,1720.76 1041.26,1720.96 1041.54,1720.96 1041.54,1720.76 1041.26,1720.76 "/>
<path clip-path="url(#clip322)" d="M1041.54 1720.96 L1041.54 1720.96 L1041.82 1720.96 L1041.82 1720.96 L1041.54 1720.96 L1041.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1041.54,1720.96 1041.54,1720.96 1041.82,1720.96 1041.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1041.82 1720.76 L1041.82 1720.96 L1042.1 1720.96 L1042.1 1720.76 L1041.82 1720.76 L1041.82 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1041.82,1720.76 1041.82,1720.96 1042.1,1720.96 1042.1,1720.76 1041.82,1720.76 "/>
<path clip-path="url(#clip322)" d="M1042.1 1720.96 L1042.1 1720.96 L1042.38 1720.96 L1042.38 1720.96 L1042.1 1720.96 L1042.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1042.1,1720.96 1042.1,1720.96 1042.38,1720.96 1042.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1042.38 1720.76 L1042.38 1720.96 L1042.66 1720.96 L1042.66 1720.76 L1042.38 1720.76 L1042.38 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1042.38,1720.76 1042.38,1720.96 1042.66,1720.96 1042.66,1720.76 1042.38,1720.76 "/>
<path clip-path="url(#clip322)" d="M1042.66 1720.76 L1042.66 1720.96 L1042.95 1720.96 L1042.95 1720.76 L1042.66 1720.76 L1042.66 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1042.66,1720.76 1042.66,1720.96 1042.95,1720.96 1042.95,1720.76 1042.66,1720.76 "/>
<path clip-path="url(#clip322)" d="M1042.95 1720.96 L1042.95 1720.96 L1043.23 1720.96 L1043.23 1720.96 L1042.95 1720.96 L1042.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1042.95,1720.96 1042.95,1720.96 1043.23,1720.96 1042.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1043.23 1720.96 L1043.23 1720.96 L1043.51 1720.96 L1043.51 1720.96 L1043.23 1720.96 L1043.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1043.23,1720.96 1043.23,1720.96 1043.51,1720.96 1043.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1043.51 1720.76 L1043.51 1720.96 L1043.79 1720.96 L1043.79 1720.76 L1043.51 1720.76 L1043.51 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1043.51,1720.76 1043.51,1720.96 1043.79,1720.96 1043.79,1720.76 1043.51,1720.76 "/>
<path clip-path="url(#clip322)" d="M1043.79 1720.76 L1043.79 1720.96 L1044.07 1720.96 L1044.07 1720.76 L1043.79 1720.76 L1043.79 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1043.79,1720.76 1043.79,1720.96 1044.07,1720.96 1044.07,1720.76 1043.79,1720.76 "/>
<path clip-path="url(#clip322)" d="M1044.07 1720.96 L1044.07 1720.96 L1044.35 1720.96 L1044.35 1720.96 L1044.07 1720.96 L1044.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1044.07,1720.96 1044.07,1720.96 1044.35,1720.96 1044.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1044.35 1720.37 L1044.35 1720.96 L1044.64 1720.96 L1044.64 1720.37 L1044.35 1720.37 L1044.35 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1044.35,1720.37 1044.35,1720.96 1044.64,1720.96 1044.64,1720.37 1044.35,1720.37 "/>
<path clip-path="url(#clip322)" d="M1044.64 1720.76 L1044.64 1720.96 L1044.92 1720.96 L1044.92 1720.76 L1044.64 1720.76 L1044.64 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1044.64,1720.76 1044.64,1720.96 1044.92,1720.96 1044.92,1720.76 1044.64,1720.76 "/>
<path clip-path="url(#clip322)" d="M1044.92 1720.76 L1044.92 1720.96 L1045.2 1720.96 L1045.2 1720.76 L1044.92 1720.76 L1044.92 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1044.92,1720.76 1044.92,1720.96 1045.2,1720.96 1045.2,1720.76 1044.92,1720.76 "/>
<path clip-path="url(#clip322)" d="M1045.2 1720.96 L1045.2 1720.96 L1045.48 1720.96 L1045.48 1720.96 L1045.2 1720.96 L1045.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1045.2,1720.96 1045.2,1720.96 1045.48,1720.96 1045.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1045.48 1720.96 L1045.48 1720.96 L1045.76 1720.96 L1045.76 1720.96 L1045.48 1720.96 L1045.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1045.48,1720.96 1045.48,1720.96 1045.76,1720.96 1045.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1045.76 1720.76 L1045.76 1720.96 L1046.04 1720.96 L1046.04 1720.76 L1045.76 1720.76 L1045.76 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1045.76,1720.76 1045.76,1720.96 1046.04,1720.96 1046.04,1720.76 1045.76,1720.76 "/>
<path clip-path="url(#clip322)" d="M1046.04 1720.76 L1046.04 1720.96 L1046.33 1720.96 L1046.33 1720.76 L1046.04 1720.76 L1046.04 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1046.04,1720.76 1046.04,1720.96 1046.33,1720.96 1046.33,1720.76 1046.04,1720.76 "/>
<path clip-path="url(#clip322)" d="M1046.33 1720.96 L1046.33 1720.96 L1046.61 1720.96 L1046.61 1720.96 L1046.33 1720.96 L1046.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1046.33,1720.96 1046.33,1720.96 1046.61,1720.96 1046.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1046.61 1720.96 L1046.61 1720.96 L1046.89 1720.96 L1046.89 1720.96 L1046.61 1720.96 L1046.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1046.61,1720.96 1046.61,1720.96 1046.89,1720.96 1046.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1046.89 1720.76 L1046.89 1720.96 L1047.17 1720.96 L1047.17 1720.76 L1046.89 1720.76 L1046.89 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1046.89,1720.76 1046.89,1720.96 1047.17,1720.96 1047.17,1720.76 1046.89,1720.76 "/>
<path clip-path="url(#clip322)" d="M1047.17 1720.96 L1047.17 1720.96 L1047.45 1720.96 L1047.45 1720.96 L1047.17 1720.96 L1047.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1047.17,1720.96 1047.17,1720.96 1047.45,1720.96 1047.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1047.45 1720.96 L1047.45 1720.96 L1047.74 1720.96 L1047.74 1720.96 L1047.45 1720.96 L1047.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1047.45,1720.96 1047.45,1720.96 1047.74,1720.96 1047.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1047.74 1720.96 L1047.74 1720.96 L1048.02 1720.96 L1048.02 1720.96 L1047.74 1720.96 L1047.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1047.74,1720.96 1047.74,1720.96 1048.02,1720.96 1047.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1048.02 1720.96 L1048.02 1720.96 L1048.3 1720.96 L1048.3 1720.96 L1048.02 1720.96 L1048.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1048.02,1720.96 1048.02,1720.96 1048.3,1720.96 1048.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1048.3 1720.76 L1048.3 1720.96 L1048.58 1720.96 L1048.58 1720.76 L1048.3 1720.76 L1048.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1048.3,1720.76 1048.3,1720.96 1048.58,1720.96 1048.58,1720.76 1048.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1048.58 1720.76 L1048.58 1720.96 L1048.86 1720.96 L1048.86 1720.76 L1048.58 1720.76 L1048.58 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1048.58,1720.76 1048.58,1720.96 1048.86,1720.96 1048.86,1720.76 1048.58,1720.76 "/>
<path clip-path="url(#clip322)" d="M1048.86 1720.96 L1048.86 1720.96 L1049.14 1720.96 L1049.14 1720.96 L1048.86 1720.96 L1048.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1048.86,1720.96 1048.86,1720.96 1049.14,1720.96 1048.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1049.14 1720.76 L1049.14 1720.96 L1049.43 1720.96 L1049.43 1720.76 L1049.14 1720.76 L1049.14 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1049.14,1720.76 1049.14,1720.96 1049.43,1720.96 1049.43,1720.76 1049.14,1720.76 "/>
<path clip-path="url(#clip322)" d="M1049.43 1720.76 L1049.43 1720.96 L1049.71 1720.96 L1049.71 1720.76 L1049.43 1720.76 L1049.43 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1049.43,1720.76 1049.43,1720.96 1049.71,1720.96 1049.71,1720.76 1049.43,1720.76 "/>
<path clip-path="url(#clip322)" d="M1049.71 1720.96 L1049.71 1720.96 L1049.99 1720.96 L1049.99 1720.96 L1049.71 1720.96 L1049.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1049.71,1720.96 1049.71,1720.96 1049.99,1720.96 1049.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1049.99 1720.96 L1049.99 1720.96 L1050.27 1720.96 L1050.27 1720.96 L1049.99 1720.96 L1049.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1049.99,1720.96 1049.99,1720.96 1050.27,1720.96 1049.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1050.27 1720.96 L1050.27 1720.96 L1050.55 1720.96 L1050.55 1720.96 L1050.27 1720.96 L1050.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1050.27,1720.96 1050.27,1720.96 1050.55,1720.96 1050.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1050.55 1720.96 L1050.55 1720.96 L1050.83 1720.96 L1050.83 1720.96 L1050.55 1720.96 L1050.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1050.55,1720.96 1050.55,1720.96 1050.83,1720.96 1050.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1050.83 1720.96 L1050.83 1720.96 L1051.12 1720.96 L1051.12 1720.96 L1050.83 1720.96 L1050.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1050.83,1720.96 1050.83,1720.96 1051.12,1720.96 1050.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1051.12 1720.96 L1051.12 1720.96 L1051.4 1720.96 L1051.4 1720.96 L1051.12 1720.96 L1051.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1051.12,1720.96 1051.12,1720.96 1051.4,1720.96 1051.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1051.4 1720.76 L1051.4 1720.96 L1051.68 1720.96 L1051.68 1720.76 L1051.4 1720.76 L1051.4 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1051.4,1720.76 1051.4,1720.96 1051.68,1720.96 1051.68,1720.76 1051.4,1720.76 "/>
<path clip-path="url(#clip322)" d="M1051.68 1720.56 L1051.68 1720.96 L1051.96 1720.96 L1051.96 1720.56 L1051.68 1720.56 L1051.68 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1051.68,1720.56 1051.68,1720.96 1051.96,1720.96 1051.96,1720.56 1051.68,1720.56 "/>
<path clip-path="url(#clip322)" d="M1051.96 1720.96 L1051.96 1720.96 L1052.24 1720.96 L1052.24 1720.96 L1051.96 1720.96 L1051.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1051.96,1720.96 1051.96,1720.96 1052.24,1720.96 1051.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1052.24 1720.96 L1052.24 1720.96 L1052.52 1720.96 L1052.52 1720.96 L1052.24 1720.96 L1052.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1052.24,1720.96 1052.24,1720.96 1052.52,1720.96 1052.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1052.52 1720.96 L1052.52 1720.96 L1052.81 1720.96 L1052.81 1720.96 L1052.52 1720.96 L1052.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1052.52,1720.96 1052.52,1720.96 1052.81,1720.96 1052.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1052.81 1720.76 L1052.81 1720.96 L1053.09 1720.96 L1053.09 1720.76 L1052.81 1720.76 L1052.81 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1052.81,1720.76 1052.81,1720.96 1053.09,1720.96 1053.09,1720.76 1052.81,1720.76 "/>
<path clip-path="url(#clip322)" d="M1053.09 1720.96 L1053.09 1720.96 L1053.37 1720.96 L1053.37 1720.96 L1053.09 1720.96 L1053.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1053.09,1720.96 1053.09,1720.96 1053.37,1720.96 1053.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1053.37 1720.96 L1053.37 1720.96 L1053.65 1720.96 L1053.65 1720.96 L1053.37 1720.96 L1053.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1053.37,1720.96 1053.37,1720.96 1053.65,1720.96 1053.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1053.65 1720.96 L1053.65 1720.96 L1053.93 1720.96 L1053.93 1720.96 L1053.65 1720.96 L1053.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1053.65,1720.96 1053.65,1720.96 1053.93,1720.96 1053.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1053.93 1720.76 L1053.93 1720.96 L1054.22 1720.96 L1054.22 1720.76 L1053.93 1720.76 L1053.93 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1053.93,1720.76 1053.93,1720.96 1054.22,1720.96 1054.22,1720.76 1053.93,1720.76 "/>
<path clip-path="url(#clip322)" d="M1054.22 1720.96 L1054.22 1720.96 L1054.5 1720.96 L1054.5 1720.96 L1054.22 1720.96 L1054.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1054.22,1720.96 1054.22,1720.96 1054.5,1720.96 1054.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1054.5 1720.96 L1054.5 1720.96 L1054.78 1720.96 L1054.78 1720.96 L1054.5 1720.96 L1054.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1054.5,1720.96 1054.5,1720.96 1054.78,1720.96 1054.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1054.78 1720.76 L1054.78 1720.96 L1055.06 1720.96 L1055.06 1720.76 L1054.78 1720.76 L1054.78 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1054.78,1720.76 1054.78,1720.96 1055.06,1720.96 1055.06,1720.76 1054.78,1720.76 "/>
<path clip-path="url(#clip322)" d="M1055.06 1720.56 L1055.06 1720.96 L1055.34 1720.96 L1055.34 1720.56 L1055.06 1720.56 L1055.06 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1055.06,1720.56 1055.06,1720.96 1055.34,1720.96 1055.34,1720.56 1055.06,1720.56 "/>
<path clip-path="url(#clip322)" d="M1055.34 1720.76 L1055.34 1720.96 L1055.62 1720.96 L1055.62 1720.76 L1055.34 1720.76 L1055.34 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1055.34,1720.76 1055.34,1720.96 1055.62,1720.96 1055.62,1720.76 1055.34,1720.76 "/>
<path clip-path="url(#clip322)" d="M1055.62 1720.76 L1055.62 1720.96 L1055.91 1720.96 L1055.91 1720.76 L1055.62 1720.76 L1055.62 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1055.62,1720.76 1055.62,1720.96 1055.91,1720.96 1055.91,1720.76 1055.62,1720.76 "/>
<path clip-path="url(#clip322)" d="M1055.91 1720.96 L1055.91 1720.96 L1056.19 1720.96 L1056.19 1720.96 L1055.91 1720.96 L1055.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1055.91,1720.96 1055.91,1720.96 1056.19,1720.96 1055.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1056.19 1720.96 L1056.19 1720.96 L1056.47 1720.96 L1056.47 1720.96 L1056.19 1720.96 L1056.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1056.19,1720.96 1056.19,1720.96 1056.47,1720.96 1056.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1056.47 1720.96 L1056.47 1720.96 L1056.75 1720.96 L1056.75 1720.96 L1056.47 1720.96 L1056.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1056.47,1720.96 1056.47,1720.96 1056.75,1720.96 1056.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1056.75 1720.96 L1056.75 1720.96 L1057.03 1720.96 L1057.03 1720.96 L1056.75 1720.96 L1056.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1056.75,1720.96 1056.75,1720.96 1057.03,1720.96 1056.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1057.03 1720.96 L1057.03 1720.96 L1057.31 1720.96 L1057.31 1720.96 L1057.03 1720.96 L1057.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1057.03,1720.96 1057.03,1720.96 1057.31,1720.96 1057.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1057.31 1720.96 L1057.31 1720.96 L1057.6 1720.96 L1057.6 1720.96 L1057.31 1720.96 L1057.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1057.31,1720.96 1057.31,1720.96 1057.6,1720.96 1057.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1057.6 1720.96 L1057.6 1720.96 L1057.88 1720.96 L1057.88 1720.96 L1057.6 1720.96 L1057.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1057.6,1720.96 1057.6,1720.96 1057.88,1720.96 1057.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1057.88 1720.96 L1057.88 1720.96 L1058.16 1720.96 L1058.16 1720.96 L1057.88 1720.96 L1057.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1057.88,1720.96 1057.88,1720.96 1058.16,1720.96 1057.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1058.16 1720.76 L1058.16 1720.96 L1058.44 1720.96 L1058.44 1720.76 L1058.16 1720.76 L1058.16 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1058.16,1720.76 1058.16,1720.96 1058.44,1720.96 1058.44,1720.76 1058.16,1720.76 "/>
<path clip-path="url(#clip322)" d="M1058.44 1720.96 L1058.44 1720.96 L1058.72 1720.96 L1058.72 1720.96 L1058.44 1720.96 L1058.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1058.44,1720.96 1058.44,1720.96 1058.72,1720.96 1058.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1058.72 1720.96 L1058.72 1720.96 L1059 1720.96 L1059 1720.96 L1058.72 1720.96 L1058.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1058.72,1720.96 1058.72,1720.96 1059,1720.96 1058.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1059 1720.96 L1059 1720.96 L1059.29 1720.96 L1059.29 1720.96 L1059 1720.96 L1059 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1059,1720.96 1059,1720.96 1059.29,1720.96 1059,1720.96 "/>
<path clip-path="url(#clip322)" d="M1059.29 1720.96 L1059.29 1720.96 L1059.57 1720.96 L1059.57 1720.96 L1059.29 1720.96 L1059.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1059.29,1720.96 1059.29,1720.96 1059.57,1720.96 1059.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1059.57 1720.96 L1059.57 1720.96 L1059.85 1720.96 L1059.85 1720.96 L1059.57 1720.96 L1059.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1059.57,1720.96 1059.57,1720.96 1059.85,1720.96 1059.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1059.85 1720.96 L1059.85 1720.96 L1060.13 1720.96 L1060.13 1720.96 L1059.85 1720.96 L1059.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1059.85,1720.96 1059.85,1720.96 1060.13,1720.96 1059.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1060.13 1720.96 L1060.13 1720.96 L1060.41 1720.96 L1060.41 1720.96 L1060.13 1720.96 L1060.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1060.13,1720.96 1060.13,1720.96 1060.41,1720.96 1060.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1060.41 1720.76 L1060.41 1720.96 L1060.69 1720.96 L1060.69 1720.76 L1060.41 1720.76 L1060.41 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1060.41,1720.76 1060.41,1720.96 1060.69,1720.96 1060.69,1720.76 1060.41,1720.76 "/>
<path clip-path="url(#clip322)" d="M1060.69 1720.76 L1060.69 1720.96 L1060.98 1720.96 L1060.98 1720.76 L1060.69 1720.76 L1060.69 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1060.69,1720.76 1060.69,1720.96 1060.98,1720.96 1060.98,1720.76 1060.69,1720.76 "/>
<path clip-path="url(#clip322)" d="M1060.98 1720.96 L1060.98 1720.96 L1061.26 1720.96 L1061.26 1720.96 L1060.98 1720.96 L1060.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1060.98,1720.96 1060.98,1720.96 1061.26,1720.96 1060.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1061.26 1720.37 L1061.26 1720.96 L1061.54 1720.96 L1061.54 1720.37 L1061.26 1720.37 L1061.26 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1061.26,1720.37 1061.26,1720.96 1061.54,1720.96 1061.54,1720.37 1061.26,1720.37 "/>
<path clip-path="url(#clip322)" d="M1061.54 1720.96 L1061.54 1720.96 L1061.82 1720.96 L1061.82 1720.96 L1061.54 1720.96 L1061.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1061.54,1720.96 1061.54,1720.96 1061.82,1720.96 1061.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1061.82 1720.96 L1061.82 1720.96 L1062.1 1720.96 L1062.1 1720.96 L1061.82 1720.96 L1061.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1061.82,1720.96 1061.82,1720.96 1062.1,1720.96 1061.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1062.1 1720.96 L1062.1 1720.96 L1062.39 1720.96 L1062.39 1720.96 L1062.1 1720.96 L1062.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1062.1,1720.96 1062.1,1720.96 1062.39,1720.96 1062.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1062.39 1720.56 L1062.39 1720.96 L1062.67 1720.96 L1062.67 1720.56 L1062.39 1720.56 L1062.39 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1062.39,1720.56 1062.39,1720.96 1062.67,1720.96 1062.67,1720.56 1062.39,1720.56 "/>
<path clip-path="url(#clip322)" d="M1062.67 1720.76 L1062.67 1720.96 L1062.95 1720.96 L1062.95 1720.76 L1062.67 1720.76 L1062.67 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1062.67,1720.76 1062.67,1720.96 1062.95,1720.96 1062.95,1720.76 1062.67,1720.76 "/>
<path clip-path="url(#clip322)" d="M1062.95 1720.76 L1062.95 1720.96 L1063.23 1720.96 L1063.23 1720.76 L1062.95 1720.76 L1062.95 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1062.95,1720.76 1062.95,1720.96 1063.23,1720.96 1063.23,1720.76 1062.95,1720.76 "/>
<path clip-path="url(#clip322)" d="M1063.23 1720.96 L1063.23 1720.96 L1063.51 1720.96 L1063.51 1720.96 L1063.23 1720.96 L1063.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1063.23,1720.96 1063.23,1720.96 1063.51,1720.96 1063.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1063.51 1720.96 L1063.51 1720.96 L1063.79 1720.96 L1063.79 1720.96 L1063.51 1720.96 L1063.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1063.51,1720.96 1063.51,1720.96 1063.79,1720.96 1063.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1063.79 1720.96 L1063.79 1720.96 L1064.08 1720.96 L1064.08 1720.96 L1063.79 1720.96 L1063.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1063.79,1720.96 1063.79,1720.96 1064.08,1720.96 1063.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1064.08 1720.76 L1064.08 1720.96 L1064.36 1720.96 L1064.36 1720.76 L1064.08 1720.76 L1064.08 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1064.08,1720.76 1064.08,1720.96 1064.36,1720.96 1064.36,1720.76 1064.08,1720.76 "/>
<path clip-path="url(#clip322)" d="M1064.36 1720.76 L1064.36 1720.96 L1064.64 1720.96 L1064.64 1720.76 L1064.36 1720.76 L1064.36 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1064.36,1720.76 1064.36,1720.96 1064.64,1720.96 1064.64,1720.76 1064.36,1720.76 "/>
<path clip-path="url(#clip322)" d="M1064.64 1720.37 L1064.64 1720.96 L1064.92 1720.96 L1064.92 1720.37 L1064.64 1720.37 L1064.64 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1064.64,1720.37 1064.64,1720.96 1064.92,1720.96 1064.92,1720.37 1064.64,1720.37 "/>
<path clip-path="url(#clip322)" d="M1064.92 1720.96 L1064.92 1720.96 L1065.2 1720.96 L1065.2 1720.96 L1064.92 1720.96 L1064.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1064.92,1720.96 1064.92,1720.96 1065.2,1720.96 1064.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1065.2 1720.96 L1065.2 1720.96 L1065.48 1720.96 L1065.48 1720.96 L1065.2 1720.96 L1065.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1065.2,1720.96 1065.2,1720.96 1065.48,1720.96 1065.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1065.48 1720.96 L1065.48 1720.96 L1065.77 1720.96 L1065.77 1720.96 L1065.48 1720.96 L1065.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1065.48,1720.96 1065.48,1720.96 1065.77,1720.96 1065.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1065.77 1720.96 L1065.77 1720.96 L1066.05 1720.96 L1066.05 1720.96 L1065.77 1720.96 L1065.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1065.77,1720.96 1065.77,1720.96 1066.05,1720.96 1065.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1066.05 1720.96 L1066.05 1720.96 L1066.33 1720.96 L1066.33 1720.96 L1066.05 1720.96 L1066.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1066.05,1720.96 1066.05,1720.96 1066.33,1720.96 1066.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1066.33 1720.96 L1066.33 1720.96 L1066.61 1720.96 L1066.61 1720.96 L1066.33 1720.96 L1066.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1066.33,1720.96 1066.33,1720.96 1066.61,1720.96 1066.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1066.61 1720.96 L1066.61 1720.96 L1066.89 1720.96 L1066.89 1720.96 L1066.61 1720.96 L1066.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1066.61,1720.96 1066.61,1720.96 1066.89,1720.96 1066.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1066.89 1720.37 L1066.89 1720.96 L1067.17 1720.96 L1067.17 1720.37 L1066.89 1720.37 L1066.89 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1066.89,1720.37 1066.89,1720.96 1067.17,1720.96 1067.17,1720.37 1066.89,1720.37 "/>
<path clip-path="url(#clip322)" d="M1067.17 1720.96 L1067.17 1720.96 L1067.46 1720.96 L1067.46 1720.96 L1067.17 1720.96 L1067.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1067.17,1720.96 1067.17,1720.96 1067.46,1720.96 1067.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1067.46 1720.96 L1067.46 1720.96 L1067.74 1720.96 L1067.74 1720.96 L1067.46 1720.96 L1067.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1067.46,1720.96 1067.46,1720.96 1067.74,1720.96 1067.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1067.74 1720.76 L1067.74 1720.96 L1068.02 1720.96 L1068.02 1720.76 L1067.74 1720.76 L1067.74 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1067.74,1720.76 1067.74,1720.96 1068.02,1720.96 1068.02,1720.76 1067.74,1720.76 "/>
<path clip-path="url(#clip322)" d="M1068.02 1720.76 L1068.02 1720.96 L1068.3 1720.96 L1068.3 1720.76 L1068.02 1720.76 L1068.02 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1068.02,1720.76 1068.02,1720.96 1068.3,1720.96 1068.3,1720.76 1068.02,1720.76 "/>
<path clip-path="url(#clip322)" d="M1068.3 1720.76 L1068.3 1720.96 L1068.58 1720.96 L1068.58 1720.76 L1068.3 1720.76 L1068.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1068.3,1720.76 1068.3,1720.96 1068.58,1720.96 1068.58,1720.76 1068.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1068.58 1720.76 L1068.58 1720.96 L1068.86 1720.96 L1068.86 1720.76 L1068.58 1720.76 L1068.58 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1068.58,1720.76 1068.58,1720.96 1068.86,1720.96 1068.86,1720.76 1068.58,1720.76 "/>
<path clip-path="url(#clip322)" d="M1068.86 1720.96 L1068.86 1720.96 L1069.15 1720.96 L1069.15 1720.96 L1068.86 1720.96 L1068.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1068.86,1720.96 1068.86,1720.96 1069.15,1720.96 1068.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1069.15 1720.96 L1069.15 1720.96 L1069.43 1720.96 L1069.43 1720.96 L1069.15 1720.96 L1069.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1069.15,1720.96 1069.15,1720.96 1069.43,1720.96 1069.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1069.43 1720.96 L1069.43 1720.96 L1069.71 1720.96 L1069.71 1720.96 L1069.43 1720.96 L1069.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1069.43,1720.96 1069.43,1720.96 1069.71,1720.96 1069.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1069.71 1720.96 L1069.71 1720.96 L1069.99 1720.96 L1069.99 1720.96 L1069.71 1720.96 L1069.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1069.71,1720.96 1069.71,1720.96 1069.99,1720.96 1069.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1069.99 1720.96 L1069.99 1720.96 L1070.27 1720.96 L1070.27 1720.96 L1069.99 1720.96 L1069.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1069.99,1720.96 1069.99,1720.96 1070.27,1720.96 1069.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1070.27 1720.96 L1070.27 1720.96 L1070.56 1720.96 L1070.56 1720.96 L1070.27 1720.96 L1070.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1070.27,1720.96 1070.27,1720.96 1070.56,1720.96 1070.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1070.56 1720.56 L1070.56 1720.96 L1070.84 1720.96 L1070.84 1720.56 L1070.56 1720.56 L1070.56 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1070.56,1720.56 1070.56,1720.96 1070.84,1720.96 1070.84,1720.56 1070.56,1720.56 "/>
<path clip-path="url(#clip322)" d="M1070.84 1720.96 L1070.84 1720.96 L1071.12 1720.96 L1071.12 1720.96 L1070.84 1720.96 L1070.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1070.84,1720.96 1070.84,1720.96 1071.12,1720.96 1070.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1071.12 1720.96 L1071.12 1720.96 L1071.4 1720.96 L1071.4 1720.96 L1071.12 1720.96 L1071.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1071.12,1720.96 1071.12,1720.96 1071.4,1720.96 1071.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1071.4 1720.96 L1071.4 1720.96 L1071.68 1720.96 L1071.68 1720.96 L1071.4 1720.96 L1071.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1071.4,1720.96 1071.4,1720.96 1071.68,1720.96 1071.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1071.68 1720.96 L1071.68 1720.96 L1071.96 1720.96 L1071.96 1720.96 L1071.68 1720.96 L1071.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1071.68,1720.96 1071.68,1720.96 1071.96,1720.96 1071.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1071.96 1720.76 L1071.96 1720.96 L1072.25 1720.96 L1072.25 1720.76 L1071.96 1720.76 L1071.96 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1071.96,1720.76 1071.96,1720.96 1072.25,1720.96 1072.25,1720.76 1071.96,1720.76 "/>
<path clip-path="url(#clip322)" d="M1072.25 1720.76 L1072.25 1720.96 L1072.53 1720.96 L1072.53 1720.76 L1072.25 1720.76 L1072.25 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1072.25,1720.76 1072.25,1720.96 1072.53,1720.96 1072.53,1720.76 1072.25,1720.76 "/>
<path clip-path="url(#clip322)" d="M1072.53 1720.96 L1072.53 1720.96 L1072.81 1720.96 L1072.81 1720.96 L1072.53 1720.96 L1072.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1072.53,1720.96 1072.53,1720.96 1072.81,1720.96 1072.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1072.81 1720.76 L1072.81 1720.96 L1073.09 1720.96 L1073.09 1720.76 L1072.81 1720.76 L1072.81 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1072.81,1720.76 1072.81,1720.96 1073.09,1720.96 1073.09,1720.76 1072.81,1720.76 "/>
<path clip-path="url(#clip322)" d="M1073.09 1720.96 L1073.09 1720.96 L1073.37 1720.96 L1073.37 1720.96 L1073.09 1720.96 L1073.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1073.09,1720.96 1073.09,1720.96 1073.37,1720.96 1073.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1073.37 1720.96 L1073.37 1720.96 L1073.65 1720.96 L1073.65 1720.96 L1073.37 1720.96 L1073.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1073.37,1720.96 1073.37,1720.96 1073.65,1720.96 1073.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1073.65 1720.96 L1073.65 1720.96 L1073.94 1720.96 L1073.94 1720.96 L1073.65 1720.96 L1073.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1073.65,1720.96 1073.65,1720.96 1073.94,1720.96 1073.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1073.94 1720.76 L1073.94 1720.96 L1074.22 1720.96 L1074.22 1720.76 L1073.94 1720.76 L1073.94 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1073.94,1720.76 1073.94,1720.96 1074.22,1720.96 1074.22,1720.76 1073.94,1720.76 "/>
<path clip-path="url(#clip322)" d="M1074.22 1720.76 L1074.22 1720.96 L1074.5 1720.96 L1074.5 1720.76 L1074.22 1720.76 L1074.22 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1074.22,1720.76 1074.22,1720.96 1074.5,1720.96 1074.5,1720.76 1074.22,1720.76 "/>
<path clip-path="url(#clip322)" d="M1074.5 1720.96 L1074.5 1720.96 L1074.78 1720.96 L1074.78 1720.96 L1074.5 1720.96 L1074.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1074.5,1720.96 1074.5,1720.96 1074.78,1720.96 1074.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1074.78 1720.96 L1074.78 1720.96 L1075.06 1720.96 L1075.06 1720.96 L1074.78 1720.96 L1074.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1074.78,1720.96 1074.78,1720.96 1075.06,1720.96 1074.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1075.06 1720.96 L1075.06 1720.96 L1075.34 1720.96 L1075.34 1720.96 L1075.06 1720.96 L1075.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1075.06,1720.96 1075.06,1720.96 1075.34,1720.96 1075.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1075.34 1720.76 L1075.34 1720.96 L1075.63 1720.96 L1075.63 1720.76 L1075.34 1720.76 L1075.34 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1075.34,1720.76 1075.34,1720.96 1075.63,1720.96 1075.63,1720.76 1075.34,1720.76 "/>
<path clip-path="url(#clip322)" d="M1075.63 1720.76 L1075.63 1720.96 L1075.91 1720.96 L1075.91 1720.76 L1075.63 1720.76 L1075.63 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1075.63,1720.76 1075.63,1720.96 1075.91,1720.96 1075.91,1720.76 1075.63,1720.76 "/>
<path clip-path="url(#clip322)" d="M1075.91 1720.96 L1075.91 1720.96 L1076.19 1720.96 L1076.19 1720.96 L1075.91 1720.96 L1075.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1075.91,1720.96 1075.91,1720.96 1076.19,1720.96 1075.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1076.19 1720.76 L1076.19 1720.96 L1076.47 1720.96 L1076.47 1720.76 L1076.19 1720.76 L1076.19 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1076.19,1720.76 1076.19,1720.96 1076.47,1720.96 1076.47,1720.76 1076.19,1720.76 "/>
<path clip-path="url(#clip322)" d="M1076.47 1720.96 L1076.47 1720.96 L1076.75 1720.96 L1076.75 1720.96 L1076.47 1720.96 L1076.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1076.47,1720.96 1076.47,1720.96 1076.75,1720.96 1076.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1076.75 1720.96 L1076.75 1720.96 L1077.03 1720.96 L1077.03 1720.96 L1076.75 1720.96 L1076.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1076.75,1720.96 1076.75,1720.96 1077.03,1720.96 1076.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1077.03 1720.96 L1077.03 1720.96 L1077.32 1720.96 L1077.32 1720.96 L1077.03 1720.96 L1077.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1077.03,1720.96 1077.03,1720.96 1077.32,1720.96 1077.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1077.32 1720.76 L1077.32 1720.96 L1077.6 1720.96 L1077.6 1720.76 L1077.32 1720.76 L1077.32 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1077.32,1720.76 1077.32,1720.96 1077.6,1720.96 1077.6,1720.76 1077.32,1720.76 "/>
<path clip-path="url(#clip322)" d="M1077.6 1720.96 L1077.6 1720.96 L1077.88 1720.96 L1077.88 1720.96 L1077.6 1720.96 L1077.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1077.6,1720.96 1077.6,1720.96 1077.88,1720.96 1077.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1077.88 1720.96 L1077.88 1720.96 L1078.16 1720.96 L1078.16 1720.96 L1077.88 1720.96 L1077.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1077.88,1720.96 1077.88,1720.96 1078.16,1720.96 1077.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1078.16 1720.96 L1078.16 1720.96 L1078.44 1720.96 L1078.44 1720.96 L1078.16 1720.96 L1078.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1078.16,1720.96 1078.16,1720.96 1078.44,1720.96 1078.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1078.44 1720.96 L1078.44 1720.96 L1078.73 1720.96 L1078.73 1720.96 L1078.44 1720.96 L1078.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1078.44,1720.96 1078.44,1720.96 1078.73,1720.96 1078.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1078.73 1720.96 L1078.73 1720.96 L1079.01 1720.96 L1079.01 1720.96 L1078.73 1720.96 L1078.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1078.73,1720.96 1078.73,1720.96 1079.01,1720.96 1078.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1079.01 1720.76 L1079.01 1720.96 L1079.29 1720.96 L1079.29 1720.76 L1079.01 1720.76 L1079.01 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1079.01,1720.76 1079.01,1720.96 1079.29,1720.96 1079.29,1720.76 1079.01,1720.76 "/>
<path clip-path="url(#clip322)" d="M1079.29 1720.96 L1079.29 1720.96 L1079.57 1720.96 L1079.57 1720.96 L1079.29 1720.96 L1079.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1079.29,1720.96 1079.29,1720.96 1079.57,1720.96 1079.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1079.57 1720.96 L1079.57 1720.96 L1079.85 1720.96 L1079.85 1720.96 L1079.57 1720.96 L1079.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1079.57,1720.96 1079.57,1720.96 1079.85,1720.96 1079.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1079.85 1720.76 L1079.85 1720.96 L1080.13 1720.96 L1080.13 1720.76 L1079.85 1720.76 L1079.85 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1079.85,1720.76 1079.85,1720.96 1080.13,1720.96 1080.13,1720.76 1079.85,1720.76 "/>
<path clip-path="url(#clip322)" d="M1080.13 1720.96 L1080.13 1720.96 L1080.42 1720.96 L1080.42 1720.96 L1080.13 1720.96 L1080.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1080.13,1720.96 1080.13,1720.96 1080.42,1720.96 1080.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1080.42 1720.56 L1080.42 1720.96 L1080.7 1720.96 L1080.7 1720.56 L1080.42 1720.56 L1080.42 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1080.42,1720.56 1080.42,1720.96 1080.7,1720.96 1080.7,1720.56 1080.42,1720.56 "/>
<path clip-path="url(#clip322)" d="M1080.7 1720.76 L1080.7 1720.96 L1080.98 1720.96 L1080.98 1720.76 L1080.7 1720.76 L1080.7 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1080.7,1720.76 1080.7,1720.96 1080.98,1720.96 1080.98,1720.76 1080.7,1720.76 "/>
<path clip-path="url(#clip322)" d="M1080.98 1720.96 L1080.98 1720.96 L1081.26 1720.96 L1081.26 1720.96 L1080.98 1720.96 L1080.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1080.98,1720.96 1080.98,1720.96 1081.26,1720.96 1080.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1081.26 1720.96 L1081.26 1720.96 L1081.54 1720.96 L1081.54 1720.96 L1081.26 1720.96 L1081.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1081.26,1720.96 1081.26,1720.96 1081.54,1720.96 1081.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1081.54 1720.96 L1081.54 1720.96 L1081.82 1720.96 L1081.82 1720.96 L1081.54 1720.96 L1081.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1081.54,1720.96 1081.54,1720.96 1081.82,1720.96 1081.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1081.82 1720.96 L1081.82 1720.96 L1082.11 1720.96 L1082.11 1720.96 L1081.82 1720.96 L1081.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1081.82,1720.96 1081.82,1720.96 1082.11,1720.96 1081.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1082.11 1720.96 L1082.11 1720.96 L1082.39 1720.96 L1082.39 1720.96 L1082.11 1720.96 L1082.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1082.11,1720.96 1082.11,1720.96 1082.39,1720.96 1082.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1082.39 1720.96 L1082.39 1720.96 L1082.67 1720.96 L1082.67 1720.96 L1082.39 1720.96 L1082.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1082.39,1720.96 1082.39,1720.96 1082.67,1720.96 1082.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1082.67 1720.96 L1082.67 1720.96 L1082.95 1720.96 L1082.95 1720.96 L1082.67 1720.96 L1082.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1082.67,1720.96 1082.67,1720.96 1082.95,1720.96 1082.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1082.95 1720.96 L1082.95 1720.96 L1083.23 1720.96 L1083.23 1720.96 L1082.95 1720.96 L1082.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1082.95,1720.96 1082.95,1720.96 1083.23,1720.96 1082.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1083.23 1720.96 L1083.23 1720.96 L1083.51 1720.96 L1083.51 1720.96 L1083.23 1720.96 L1083.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1083.23,1720.96 1083.23,1720.96 1083.51,1720.96 1083.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1083.51 1720.96 L1083.51 1720.96 L1083.8 1720.96 L1083.8 1720.96 L1083.51 1720.96 L1083.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1083.51,1720.96 1083.51,1720.96 1083.8,1720.96 1083.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1083.8 1720.96 L1083.8 1720.96 L1084.08 1720.96 L1084.08 1720.96 L1083.8 1720.96 L1083.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1083.8,1720.96 1083.8,1720.96 1084.08,1720.96 1083.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1084.08 1720.96 L1084.08 1720.96 L1084.36 1720.96 L1084.36 1720.96 L1084.08 1720.96 L1084.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1084.08,1720.96 1084.08,1720.96 1084.36,1720.96 1084.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1084.36 1720.96 L1084.36 1720.96 L1084.64 1720.96 L1084.64 1720.96 L1084.36 1720.96 L1084.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1084.36,1720.96 1084.36,1720.96 1084.64,1720.96 1084.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1084.64 1720.76 L1084.64 1720.96 L1084.92 1720.96 L1084.92 1720.76 L1084.64 1720.76 L1084.64 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1084.64,1720.76 1084.64,1720.96 1084.92,1720.96 1084.92,1720.76 1084.64,1720.76 "/>
<path clip-path="url(#clip322)" d="M1084.92 1720.96 L1084.92 1720.96 L1085.2 1720.96 L1085.2 1720.96 L1084.92 1720.96 L1084.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1084.92,1720.96 1084.92,1720.96 1085.2,1720.96 1084.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1085.2 1720.96 L1085.2 1720.96 L1085.49 1720.96 L1085.49 1720.96 L1085.2 1720.96 L1085.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1085.2,1720.96 1085.2,1720.96 1085.49,1720.96 1085.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1085.49 1720.96 L1085.49 1720.96 L1085.77 1720.96 L1085.77 1720.96 L1085.49 1720.96 L1085.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1085.49,1720.96 1085.49,1720.96 1085.77,1720.96 1085.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1085.77 1720.76 L1085.77 1720.96 L1086.05 1720.96 L1086.05 1720.76 L1085.77 1720.76 L1085.77 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1085.77,1720.76 1085.77,1720.96 1086.05,1720.96 1086.05,1720.76 1085.77,1720.76 "/>
<path clip-path="url(#clip322)" d="M1086.05 1720.96 L1086.05 1720.96 L1086.33 1720.96 L1086.33 1720.96 L1086.05 1720.96 L1086.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1086.05,1720.96 1086.05,1720.96 1086.33,1720.96 1086.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1086.33 1720.96 L1086.33 1720.96 L1086.61 1720.96 L1086.61 1720.96 L1086.33 1720.96 L1086.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1086.33,1720.96 1086.33,1720.96 1086.61,1720.96 1086.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1086.61 1720.96 L1086.61 1720.96 L1086.9 1720.96 L1086.9 1720.96 L1086.61 1720.96 L1086.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1086.61,1720.96 1086.61,1720.96 1086.9,1720.96 1086.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1086.9 1720.76 L1086.9 1720.96 L1087.18 1720.96 L1087.18 1720.76 L1086.9 1720.76 L1086.9 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1086.9,1720.76 1086.9,1720.96 1087.18,1720.96 1087.18,1720.76 1086.9,1720.76 "/>
<path clip-path="url(#clip322)" d="M1087.18 1720.96 L1087.18 1720.96 L1087.46 1720.96 L1087.46 1720.96 L1087.18 1720.96 L1087.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1087.18,1720.96 1087.18,1720.96 1087.46,1720.96 1087.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1087.46 1720.96 L1087.46 1720.96 L1087.74 1720.96 L1087.74 1720.96 L1087.46 1720.96 L1087.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1087.46,1720.96 1087.46,1720.96 1087.74,1720.96 1087.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1087.74 1720.76 L1087.74 1720.96 L1088.02 1720.96 L1088.02 1720.76 L1087.74 1720.76 L1087.74 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1087.74,1720.76 1087.74,1720.96 1088.02,1720.96 1088.02,1720.76 1087.74,1720.76 "/>
<path clip-path="url(#clip322)" d="M1088.02 1720.76 L1088.02 1720.96 L1088.3 1720.96 L1088.3 1720.76 L1088.02 1720.76 L1088.02 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1088.02,1720.76 1088.02,1720.96 1088.3,1720.96 1088.3,1720.76 1088.02,1720.76 "/>
<path clip-path="url(#clip322)" d="M1088.3 1720.76 L1088.3 1720.96 L1088.59 1720.96 L1088.59 1720.76 L1088.3 1720.76 L1088.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1088.3,1720.76 1088.3,1720.96 1088.59,1720.96 1088.59,1720.76 1088.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1088.59 1720.96 L1088.59 1720.96 L1088.87 1720.96 L1088.87 1720.96 L1088.59 1720.96 L1088.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1088.59,1720.96 1088.59,1720.96 1088.87,1720.96 1088.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1088.87 1720.76 L1088.87 1720.96 L1089.15 1720.96 L1089.15 1720.76 L1088.87 1720.76 L1088.87 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1088.87,1720.76 1088.87,1720.96 1089.15,1720.96 1089.15,1720.76 1088.87,1720.76 "/>
<path clip-path="url(#clip322)" d="M1089.15 1720.96 L1089.15 1720.96 L1089.43 1720.96 L1089.43 1720.96 L1089.15 1720.96 L1089.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1089.15,1720.96 1089.15,1720.96 1089.43,1720.96 1089.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1089.43 1720.96 L1089.43 1720.96 L1089.71 1720.96 L1089.71 1720.96 L1089.43 1720.96 L1089.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1089.43,1720.96 1089.43,1720.96 1089.71,1720.96 1089.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1089.71 1720.76 L1089.71 1720.96 L1089.99 1720.96 L1089.99 1720.76 L1089.71 1720.76 L1089.71 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1089.71,1720.76 1089.71,1720.96 1089.99,1720.96 1089.99,1720.76 1089.71,1720.76 "/>
<path clip-path="url(#clip322)" d="M1089.99 1720.96 L1089.99 1720.96 L1090.28 1720.96 L1090.28 1720.96 L1089.99 1720.96 L1089.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1089.99,1720.96 1089.99,1720.96 1090.28,1720.96 1089.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1090.28 1720.96 L1090.28 1720.96 L1090.56 1720.96 L1090.56 1720.96 L1090.28 1720.96 L1090.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1090.28,1720.96 1090.28,1720.96 1090.56,1720.96 1090.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1090.56 1720.96 L1090.56 1720.96 L1090.84 1720.96 L1090.84 1720.96 L1090.56 1720.96 L1090.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1090.56,1720.96 1090.56,1720.96 1090.84,1720.96 1090.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1090.84 1720.96 L1090.84 1720.96 L1091.12 1720.96 L1091.12 1720.96 L1090.84 1720.96 L1090.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1090.84,1720.96 1090.84,1720.96 1091.12,1720.96 1090.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1091.12 1720.96 L1091.12 1720.96 L1091.4 1720.96 L1091.4 1720.96 L1091.12 1720.96 L1091.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1091.12,1720.96 1091.12,1720.96 1091.4,1720.96 1091.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1091.4 1720.96 L1091.4 1720.96 L1091.68 1720.96 L1091.68 1720.96 L1091.4 1720.96 L1091.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1091.4,1720.96 1091.4,1720.96 1091.68,1720.96 1091.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1091.68 1720.76 L1091.68 1720.96 L1091.97 1720.96 L1091.97 1720.76 L1091.68 1720.76 L1091.68 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1091.68,1720.76 1091.68,1720.96 1091.97,1720.96 1091.97,1720.76 1091.68,1720.76 "/>
<path clip-path="url(#clip322)" d="M1091.97 1720.96 L1091.97 1720.96 L1092.25 1720.96 L1092.25 1720.96 L1091.97 1720.96 L1091.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1091.97,1720.96 1091.97,1720.96 1092.25,1720.96 1091.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1092.25 1720.96 L1092.25 1720.96 L1092.53 1720.96 L1092.53 1720.96 L1092.25 1720.96 L1092.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1092.25,1720.96 1092.25,1720.96 1092.53,1720.96 1092.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1092.53 1720.96 L1092.53 1720.96 L1092.81 1720.96 L1092.81 1720.96 L1092.53 1720.96 L1092.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1092.53,1720.96 1092.53,1720.96 1092.81,1720.96 1092.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1092.81 1720.96 L1092.81 1720.96 L1093.09 1720.96 L1093.09 1720.96 L1092.81 1720.96 L1092.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1092.81,1720.96 1092.81,1720.96 1093.09,1720.96 1092.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1093.09 1720.76 L1093.09 1720.96 L1093.37 1720.96 L1093.37 1720.76 L1093.09 1720.76 L1093.09 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1093.09,1720.76 1093.09,1720.96 1093.37,1720.96 1093.37,1720.76 1093.09,1720.76 "/>
<path clip-path="url(#clip322)" d="M1093.37 1720.96 L1093.37 1720.96 L1093.66 1720.96 L1093.66 1720.96 L1093.37 1720.96 L1093.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1093.37,1720.96 1093.37,1720.96 1093.66,1720.96 1093.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1093.66 1720.76 L1093.66 1720.96 L1093.94 1720.96 L1093.94 1720.76 L1093.66 1720.76 L1093.66 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1093.66,1720.76 1093.66,1720.96 1093.94,1720.96 1093.94,1720.76 1093.66,1720.76 "/>
<path clip-path="url(#clip322)" d="M1093.94 1720.76 L1093.94 1720.96 L1094.22 1720.96 L1094.22 1720.76 L1093.94 1720.76 L1093.94 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1093.94,1720.76 1093.94,1720.96 1094.22,1720.96 1094.22,1720.76 1093.94,1720.76 "/>
<path clip-path="url(#clip322)" d="M1094.22 1720.56 L1094.22 1720.96 L1094.5 1720.96 L1094.5 1720.56 L1094.22 1720.56 L1094.22 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1094.22,1720.56 1094.22,1720.96 1094.5,1720.96 1094.5,1720.56 1094.22,1720.56 "/>
<path clip-path="url(#clip322)" d="M1094.5 1720.76 L1094.5 1720.96 L1094.78 1720.96 L1094.78 1720.76 L1094.5 1720.76 L1094.5 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1094.5,1720.76 1094.5,1720.96 1094.78,1720.96 1094.78,1720.76 1094.5,1720.76 "/>
<path clip-path="url(#clip322)" d="M1094.78 1720.96 L1094.78 1720.96 L1095.07 1720.96 L1095.07 1720.96 L1094.78 1720.96 L1094.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1094.78,1720.96 1094.78,1720.96 1095.07,1720.96 1094.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1095.07 1720.76 L1095.07 1720.96 L1095.35 1720.96 L1095.35 1720.76 L1095.07 1720.76 L1095.07 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1095.07,1720.76 1095.07,1720.96 1095.35,1720.96 1095.35,1720.76 1095.07,1720.76 "/>
<path clip-path="url(#clip322)" d="M1095.35 1720.96 L1095.35 1720.96 L1095.63 1720.96 L1095.63 1720.96 L1095.35 1720.96 L1095.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1095.35,1720.96 1095.35,1720.96 1095.63,1720.96 1095.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1095.63 1720.76 L1095.63 1720.96 L1095.91 1720.96 L1095.91 1720.76 L1095.63 1720.76 L1095.63 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1095.63,1720.76 1095.63,1720.96 1095.91,1720.96 1095.91,1720.76 1095.63,1720.76 "/>
<path clip-path="url(#clip322)" d="M1095.91 1720.76 L1095.91 1720.96 L1096.19 1720.96 L1096.19 1720.76 L1095.91 1720.76 L1095.91 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1095.91,1720.76 1095.91,1720.96 1096.19,1720.96 1096.19,1720.76 1095.91,1720.76 "/>
<path clip-path="url(#clip322)" d="M1096.19 1720.96 L1096.19 1720.96 L1096.47 1720.96 L1096.47 1720.96 L1096.19 1720.96 L1096.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1096.19,1720.96 1096.19,1720.96 1096.47,1720.96 1096.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1096.47 1720.96 L1096.47 1720.96 L1096.76 1720.96 L1096.76 1720.96 L1096.47 1720.96 L1096.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1096.47,1720.96 1096.47,1720.96 1096.76,1720.96 1096.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1096.76 1720.96 L1096.76 1720.96 L1097.04 1720.96 L1097.04 1720.96 L1096.76 1720.96 L1096.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1096.76,1720.96 1096.76,1720.96 1097.04,1720.96 1096.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1097.04 1720.76 L1097.04 1720.96 L1097.32 1720.96 L1097.32 1720.76 L1097.04 1720.76 L1097.04 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1097.04,1720.76 1097.04,1720.96 1097.32,1720.96 1097.32,1720.76 1097.04,1720.76 "/>
<path clip-path="url(#clip322)" d="M1097.32 1720.96 L1097.32 1720.96 L1097.6 1720.96 L1097.6 1720.96 L1097.32 1720.96 L1097.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1097.32,1720.96 1097.32,1720.96 1097.6,1720.96 1097.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1097.6 1720.96 L1097.6 1720.96 L1097.88 1720.96 L1097.88 1720.96 L1097.6 1720.96 L1097.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1097.6,1720.96 1097.6,1720.96 1097.88,1720.96 1097.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1097.88 1720.96 L1097.88 1720.96 L1098.16 1720.96 L1098.16 1720.96 L1097.88 1720.96 L1097.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1097.88,1720.96 1097.88,1720.96 1098.16,1720.96 1097.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1098.16 1720.76 L1098.16 1720.96 L1098.45 1720.96 L1098.45 1720.76 L1098.16 1720.76 L1098.16 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1098.16,1720.76 1098.16,1720.96 1098.45,1720.96 1098.45,1720.76 1098.16,1720.76 "/>
<path clip-path="url(#clip322)" d="M1098.45 1720.96 L1098.45 1720.96 L1098.73 1720.96 L1098.73 1720.96 L1098.45 1720.96 L1098.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1098.45,1720.96 1098.45,1720.96 1098.73,1720.96 1098.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1098.73 1720.96 L1098.73 1720.96 L1099.01 1720.96 L1099.01 1720.96 L1098.73 1720.96 L1098.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1098.73,1720.96 1098.73,1720.96 1099.01,1720.96 1098.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1099.01 1720.96 L1099.01 1720.96 L1099.29 1720.96 L1099.29 1720.96 L1099.01 1720.96 L1099.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1099.01,1720.96 1099.01,1720.96 1099.29,1720.96 1099.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1099.29 1720.96 L1099.29 1720.96 L1099.57 1720.96 L1099.57 1720.96 L1099.29 1720.96 L1099.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1099.29,1720.96 1099.29,1720.96 1099.57,1720.96 1099.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1099.57 1720.76 L1099.57 1720.96 L1099.85 1720.96 L1099.85 1720.76 L1099.57 1720.76 L1099.57 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1099.57,1720.76 1099.57,1720.96 1099.85,1720.96 1099.85,1720.76 1099.57,1720.76 "/>
<path clip-path="url(#clip322)" d="M1099.85 1720.96 L1099.85 1720.96 L1100.14 1720.96 L1100.14 1720.96 L1099.85 1720.96 L1099.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1099.85,1720.96 1099.85,1720.96 1100.14,1720.96 1099.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1100.14 1720.96 L1100.14 1720.96 L1100.42 1720.96 L1100.42 1720.96 L1100.14 1720.96 L1100.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1100.14,1720.96 1100.14,1720.96 1100.42,1720.96 1100.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1100.42 1720.96 L1100.42 1720.96 L1100.7 1720.96 L1100.7 1720.96 L1100.42 1720.96 L1100.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1100.42,1720.96 1100.42,1720.96 1100.7,1720.96 1100.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1100.7 1720.96 L1100.7 1720.96 L1100.98 1720.96 L1100.98 1720.96 L1100.7 1720.96 L1100.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1100.7,1720.96 1100.7,1720.96 1100.98,1720.96 1100.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1100.98 1720.96 L1100.98 1720.96 L1101.26 1720.96 L1101.26 1720.96 L1100.98 1720.96 L1100.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1100.98,1720.96 1100.98,1720.96 1101.26,1720.96 1100.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1101.26 1720.96 L1101.26 1720.96 L1101.54 1720.96 L1101.54 1720.96 L1101.26 1720.96 L1101.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1101.26,1720.96 1101.26,1720.96 1101.54,1720.96 1101.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1101.54 1720.96 L1101.54 1720.96 L1101.83 1720.96 L1101.83 1720.96 L1101.54 1720.96 L1101.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1101.54,1720.96 1101.54,1720.96 1101.83,1720.96 1101.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1101.83 1720.96 L1101.83 1720.96 L1102.11 1720.96 L1102.11 1720.96 L1101.83 1720.96 L1101.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1101.83,1720.96 1101.83,1720.96 1102.11,1720.96 1101.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1102.11 1720.96 L1102.11 1720.96 L1102.39 1720.96 L1102.39 1720.96 L1102.11 1720.96 L1102.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1102.11,1720.96 1102.11,1720.96 1102.39,1720.96 1102.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1102.39 1720.96 L1102.39 1720.96 L1102.67 1720.96 L1102.67 1720.96 L1102.39 1720.96 L1102.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1102.39,1720.96 1102.39,1720.96 1102.67,1720.96 1102.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1102.67 1720.56 L1102.67 1720.96 L1102.95 1720.96 L1102.95 1720.56 L1102.67 1720.56 L1102.67 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1102.67,1720.56 1102.67,1720.96 1102.95,1720.96 1102.95,1720.56 1102.67,1720.56 "/>
<path clip-path="url(#clip322)" d="M1102.95 1720.96 L1102.95 1720.96 L1103.24 1720.96 L1103.24 1720.96 L1102.95 1720.96 L1102.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1102.95,1720.96 1102.95,1720.96 1103.24,1720.96 1102.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1103.24 1720.96 L1103.24 1720.96 L1103.52 1720.96 L1103.52 1720.96 L1103.24 1720.96 L1103.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1103.24,1720.96 1103.24,1720.96 1103.52,1720.96 1103.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1103.52 1720.96 L1103.52 1720.96 L1103.8 1720.96 L1103.8 1720.96 L1103.52 1720.96 L1103.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1103.52,1720.96 1103.52,1720.96 1103.8,1720.96 1103.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1103.8 1720.96 L1103.8 1720.96 L1104.08 1720.96 L1104.08 1720.96 L1103.8 1720.96 L1103.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1103.8,1720.96 1103.8,1720.96 1104.08,1720.96 1103.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1104.08 1720.96 L1104.08 1720.96 L1104.36 1720.96 L1104.36 1720.96 L1104.08 1720.96 L1104.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1104.08,1720.96 1104.08,1720.96 1104.36,1720.96 1104.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1104.36 1720.96 L1104.36 1720.96 L1104.64 1720.96 L1104.64 1720.96 L1104.36 1720.96 L1104.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1104.36,1720.96 1104.36,1720.96 1104.64,1720.96 1104.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1104.64 1720.96 L1104.64 1720.96 L1104.93 1720.96 L1104.93 1720.96 L1104.64 1720.96 L1104.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1104.64,1720.96 1104.64,1720.96 1104.93,1720.96 1104.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1104.93 1720.96 L1104.93 1720.96 L1105.21 1720.96 L1105.21 1720.96 L1104.93 1720.96 L1104.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1104.93,1720.96 1104.93,1720.96 1105.21,1720.96 1104.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1105.21 1720.96 L1105.21 1720.96 L1105.49 1720.96 L1105.49 1720.96 L1105.21 1720.96 L1105.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1105.21,1720.96 1105.21,1720.96 1105.49,1720.96 1105.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1105.49 1720.96 L1105.49 1720.96 L1105.77 1720.96 L1105.77 1720.96 L1105.49 1720.96 L1105.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1105.49,1720.96 1105.49,1720.96 1105.77,1720.96 1105.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1105.77 1720.96 L1105.77 1720.96 L1106.05 1720.96 L1106.05 1720.96 L1105.77 1720.96 L1105.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1105.77,1720.96 1105.77,1720.96 1106.05,1720.96 1105.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1106.05 1720.76 L1106.05 1720.96 L1106.33 1720.96 L1106.33 1720.76 L1106.05 1720.76 L1106.05 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1106.05,1720.76 1106.05,1720.96 1106.33,1720.96 1106.33,1720.76 1106.05,1720.76 "/>
<path clip-path="url(#clip322)" d="M1106.33 1720.96 L1106.33 1720.96 L1106.62 1720.96 L1106.62 1720.96 L1106.33 1720.96 L1106.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1106.33,1720.96 1106.33,1720.96 1106.62,1720.96 1106.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1106.62 1720.96 L1106.62 1720.96 L1106.9 1720.96 L1106.9 1720.96 L1106.62 1720.96 L1106.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1106.62,1720.96 1106.62,1720.96 1106.9,1720.96 1106.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1106.9 1720.96 L1106.9 1720.96 L1107.18 1720.96 L1107.18 1720.96 L1106.9 1720.96 L1106.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1106.9,1720.96 1106.9,1720.96 1107.18,1720.96 1106.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1107.18 1720.37 L1107.18 1720.96 L1107.46 1720.96 L1107.46 1720.37 L1107.18 1720.37 L1107.18 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1107.18,1720.37 1107.18,1720.96 1107.46,1720.96 1107.46,1720.37 1107.18,1720.37 "/>
<path clip-path="url(#clip322)" d="M1107.46 1720.76 L1107.46 1720.96 L1107.74 1720.96 L1107.74 1720.76 L1107.46 1720.76 L1107.46 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1107.46,1720.76 1107.46,1720.96 1107.74,1720.96 1107.74,1720.76 1107.46,1720.76 "/>
<path clip-path="url(#clip322)" d="M1107.74 1720.76 L1107.74 1720.96 L1108.02 1720.96 L1108.02 1720.76 L1107.74 1720.76 L1107.74 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1107.74,1720.76 1107.74,1720.96 1108.02,1720.96 1108.02,1720.76 1107.74,1720.76 "/>
<path clip-path="url(#clip322)" d="M1108.02 1720.96 L1108.02 1720.96 L1108.31 1720.96 L1108.31 1720.96 L1108.02 1720.96 L1108.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1108.02,1720.96 1108.02,1720.96 1108.31,1720.96 1108.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1108.31 1720.96 L1108.31 1720.96 L1108.59 1720.96 L1108.59 1720.96 L1108.31 1720.96 L1108.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1108.31,1720.96 1108.31,1720.96 1108.59,1720.96 1108.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1108.59 1720.96 L1108.59 1720.96 L1108.87 1720.96 L1108.87 1720.96 L1108.59 1720.96 L1108.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1108.59,1720.96 1108.59,1720.96 1108.87,1720.96 1108.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1108.87 1720.96 L1108.87 1720.96 L1109.15 1720.96 L1109.15 1720.96 L1108.87 1720.96 L1108.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1108.87,1720.96 1108.87,1720.96 1109.15,1720.96 1108.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1109.15 1720.96 L1109.15 1720.96 L1109.43 1720.96 L1109.43 1720.96 L1109.15 1720.96 L1109.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1109.15,1720.96 1109.15,1720.96 1109.43,1720.96 1109.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1109.43 1720.96 L1109.43 1720.96 L1109.71 1720.96 L1109.71 1720.96 L1109.43 1720.96 L1109.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1109.43,1720.96 1109.43,1720.96 1109.71,1720.96 1109.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1109.71 1720.96 L1109.71 1720.96 L1110 1720.96 L1110 1720.96 L1109.71 1720.96 L1109.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1109.71,1720.96 1109.71,1720.96 1110,1720.96 1109.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1110 1720.96 L1110 1720.96 L1110.28 1720.96 L1110.28 1720.96 L1110 1720.96 L1110 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1110,1720.96 1110,1720.96 1110.28,1720.96 1110,1720.96 "/>
<path clip-path="url(#clip322)" d="M1110.28 1720.96 L1110.28 1720.96 L1110.56 1720.96 L1110.56 1720.96 L1110.28 1720.96 L1110.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1110.28,1720.96 1110.28,1720.96 1110.56,1720.96 1110.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1110.56 1720.96 L1110.56 1720.96 L1110.84 1720.96 L1110.84 1720.96 L1110.56 1720.96 L1110.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1110.56,1720.96 1110.56,1720.96 1110.84,1720.96 1110.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1110.84 1720.96 L1110.84 1720.96 L1111.12 1720.96 L1111.12 1720.96 L1110.84 1720.96 L1110.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1110.84,1720.96 1110.84,1720.96 1111.12,1720.96 1110.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1111.12 1720.96 L1111.12 1720.96 L1111.41 1720.96 L1111.41 1720.96 L1111.12 1720.96 L1111.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1111.12,1720.96 1111.12,1720.96 1111.41,1720.96 1111.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1111.41 1720.96 L1111.41 1720.96 L1111.69 1720.96 L1111.69 1720.96 L1111.41 1720.96 L1111.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1111.41,1720.96 1111.41,1720.96 1111.69,1720.96 1111.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1111.69 1720.96 L1111.69 1720.96 L1111.97 1720.96 L1111.97 1720.96 L1111.69 1720.96 L1111.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1111.69,1720.96 1111.69,1720.96 1111.97,1720.96 1111.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1111.97 1720.76 L1111.97 1720.96 L1112.25 1720.96 L1112.25 1720.76 L1111.97 1720.76 L1111.97 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1111.97,1720.76 1111.97,1720.96 1112.25,1720.96 1112.25,1720.76 1111.97,1720.76 "/>
<path clip-path="url(#clip322)" d="M1112.25 1720.56 L1112.25 1720.96 L1112.53 1720.96 L1112.53 1720.56 L1112.25 1720.56 L1112.25 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1112.25,1720.56 1112.25,1720.96 1112.53,1720.96 1112.53,1720.56 1112.25,1720.56 "/>
<path clip-path="url(#clip322)" d="M1112.53 1720.96 L1112.53 1720.96 L1112.81 1720.96 L1112.81 1720.96 L1112.53 1720.96 L1112.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1112.53,1720.96 1112.53,1720.96 1112.81,1720.96 1112.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1112.81 1720.76 L1112.81 1720.96 L1113.1 1720.96 L1113.1 1720.76 L1112.81 1720.76 L1112.81 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1112.81,1720.76 1112.81,1720.96 1113.1,1720.96 1113.1,1720.76 1112.81,1720.76 "/>
<path clip-path="url(#clip322)" d="M1113.1 1720.96 L1113.1 1720.96 L1113.38 1720.96 L1113.38 1720.96 L1113.1 1720.96 L1113.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1113.1,1720.96 1113.1,1720.96 1113.38,1720.96 1113.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1113.38 1720.96 L1113.38 1720.96 L1113.66 1720.96 L1113.66 1720.96 L1113.38 1720.96 L1113.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1113.38,1720.96 1113.38,1720.96 1113.66,1720.96 1113.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1113.66 1720.96 L1113.66 1720.96 L1113.94 1720.96 L1113.94 1720.96 L1113.66 1720.96 L1113.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1113.66,1720.96 1113.66,1720.96 1113.94,1720.96 1113.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1113.94 1720.96 L1113.94 1720.96 L1114.22 1720.96 L1114.22 1720.96 L1113.94 1720.96 L1113.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1113.94,1720.96 1113.94,1720.96 1114.22,1720.96 1113.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1114.22 1720.76 L1114.22 1720.96 L1114.5 1720.96 L1114.5 1720.76 L1114.22 1720.76 L1114.22 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1114.22,1720.76 1114.22,1720.96 1114.5,1720.96 1114.5,1720.76 1114.22,1720.76 "/>
<path clip-path="url(#clip322)" d="M1114.5 1720.96 L1114.5 1720.96 L1114.79 1720.96 L1114.79 1720.96 L1114.5 1720.96 L1114.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1114.5,1720.96 1114.5,1720.96 1114.79,1720.96 1114.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1114.79 1720.96 L1114.79 1720.96 L1115.07 1720.96 L1115.07 1720.96 L1114.79 1720.96 L1114.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1114.79,1720.96 1114.79,1720.96 1115.07,1720.96 1114.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1115.07 1720.96 L1115.07 1720.96 L1115.35 1720.96 L1115.35 1720.96 L1115.07 1720.96 L1115.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1115.07,1720.96 1115.07,1720.96 1115.35,1720.96 1115.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1115.35 1720.56 L1115.35 1720.96 L1115.63 1720.96 L1115.63 1720.56 L1115.35 1720.56 L1115.35 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1115.35,1720.56 1115.35,1720.96 1115.63,1720.96 1115.63,1720.56 1115.35,1720.56 "/>
<path clip-path="url(#clip322)" d="M1115.63 1720.96 L1115.63 1720.96 L1115.91 1720.96 L1115.91 1720.96 L1115.63 1720.96 L1115.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1115.63,1720.96 1115.63,1720.96 1115.91,1720.96 1115.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1115.91 1720.96 L1115.91 1720.96 L1116.19 1720.96 L1116.19 1720.96 L1115.91 1720.96 L1115.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1115.91,1720.96 1115.91,1720.96 1116.19,1720.96 1115.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1116.19 1720.76 L1116.19 1720.96 L1116.48 1720.96 L1116.48 1720.76 L1116.19 1720.76 L1116.19 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1116.19,1720.76 1116.19,1720.96 1116.48,1720.96 1116.48,1720.76 1116.19,1720.76 "/>
<path clip-path="url(#clip322)" d="M1116.48 1720.76 L1116.48 1720.96 L1116.76 1720.96 L1116.76 1720.76 L1116.48 1720.76 L1116.48 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1116.48,1720.76 1116.48,1720.96 1116.76,1720.96 1116.76,1720.76 1116.48,1720.76 "/>
<path clip-path="url(#clip322)" d="M1116.76 1720.96 L1116.76 1720.96 L1117.04 1720.96 L1117.04 1720.96 L1116.76 1720.96 L1116.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1116.76,1720.96 1116.76,1720.96 1117.04,1720.96 1116.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1117.04 1720.96 L1117.04 1720.96 L1117.32 1720.96 L1117.32 1720.96 L1117.04 1720.96 L1117.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1117.04,1720.96 1117.04,1720.96 1117.32,1720.96 1117.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1117.32 1720.96 L1117.32 1720.96 L1117.6 1720.96 L1117.6 1720.96 L1117.32 1720.96 L1117.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1117.32,1720.96 1117.32,1720.96 1117.6,1720.96 1117.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1117.6 1720.96 L1117.6 1720.96 L1117.89 1720.96 L1117.89 1720.96 L1117.6 1720.96 L1117.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1117.6,1720.96 1117.6,1720.96 1117.89,1720.96 1117.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1117.89 1720.96 L1117.89 1720.96 L1118.17 1720.96 L1118.17 1720.96 L1117.89 1720.96 L1117.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1117.89,1720.96 1117.89,1720.96 1118.17,1720.96 1117.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1118.17 1720.76 L1118.17 1720.96 L1118.45 1720.96 L1118.45 1720.76 L1118.17 1720.76 L1118.17 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1118.17,1720.76 1118.17,1720.96 1118.45,1720.96 1118.45,1720.76 1118.17,1720.76 "/>
<path clip-path="url(#clip322)" d="M1118.45 1720.96 L1118.45 1720.96 L1118.73 1720.96 L1118.73 1720.96 L1118.45 1720.96 L1118.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1118.45,1720.96 1118.45,1720.96 1118.73,1720.96 1118.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1118.73 1720.96 L1118.73 1720.96 L1119.01 1720.96 L1119.01 1720.96 L1118.73 1720.96 L1118.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1118.73,1720.96 1118.73,1720.96 1119.01,1720.96 1118.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1119.01 1720.96 L1119.01 1720.96 L1119.29 1720.96 L1119.29 1720.96 L1119.01 1720.96 L1119.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1119.01,1720.96 1119.01,1720.96 1119.29,1720.96 1119.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1119.29 1720.96 L1119.29 1720.96 L1119.58 1720.96 L1119.58 1720.96 L1119.29 1720.96 L1119.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1119.29,1720.96 1119.29,1720.96 1119.58,1720.96 1119.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1119.58 1720.96 L1119.58 1720.96 L1119.86 1720.96 L1119.86 1720.96 L1119.58 1720.96 L1119.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1119.58,1720.96 1119.58,1720.96 1119.86,1720.96 1119.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1119.86 1720.76 L1119.86 1720.96 L1120.14 1720.96 L1120.14 1720.76 L1119.86 1720.76 L1119.86 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1119.86,1720.76 1119.86,1720.96 1120.14,1720.96 1120.14,1720.76 1119.86,1720.76 "/>
<path clip-path="url(#clip322)" d="M1120.14 1720.96 L1120.14 1720.96 L1120.42 1720.96 L1120.42 1720.96 L1120.14 1720.96 L1120.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1120.14,1720.96 1120.14,1720.96 1120.42,1720.96 1120.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1120.42 1720.56 L1120.42 1720.96 L1120.7 1720.96 L1120.7 1720.56 L1120.42 1720.56 L1120.42 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1120.42,1720.56 1120.42,1720.96 1120.7,1720.96 1120.7,1720.56 1120.42,1720.56 "/>
<path clip-path="url(#clip322)" d="M1120.7 1720.96 L1120.7 1720.96 L1120.98 1720.96 L1120.98 1720.96 L1120.7 1720.96 L1120.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1120.7,1720.96 1120.7,1720.96 1120.98,1720.96 1120.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1120.98 1720.76 L1120.98 1720.96 L1121.27 1720.96 L1121.27 1720.76 L1120.98 1720.76 L1120.98 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1120.98,1720.76 1120.98,1720.96 1121.27,1720.96 1121.27,1720.76 1120.98,1720.76 "/>
<path clip-path="url(#clip322)" d="M1121.27 1720.96 L1121.27 1720.96 L1121.55 1720.96 L1121.55 1720.96 L1121.27 1720.96 L1121.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1121.27,1720.96 1121.27,1720.96 1121.55,1720.96 1121.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1121.55 1720.96 L1121.55 1720.96 L1121.83 1720.96 L1121.83 1720.96 L1121.55 1720.96 L1121.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1121.55,1720.96 1121.55,1720.96 1121.83,1720.96 1121.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1121.83 1720.76 L1121.83 1720.96 L1122.11 1720.96 L1122.11 1720.76 L1121.83 1720.76 L1121.83 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1121.83,1720.76 1121.83,1720.96 1122.11,1720.96 1122.11,1720.76 1121.83,1720.76 "/>
<path clip-path="url(#clip322)" d="M1122.11 1720.96 L1122.11 1720.96 L1122.39 1720.96 L1122.39 1720.96 L1122.11 1720.96 L1122.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1122.11,1720.96 1122.11,1720.96 1122.39,1720.96 1122.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1122.39 1720.56 L1122.39 1720.96 L1122.67 1720.96 L1122.67 1720.56 L1122.39 1720.56 L1122.39 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1122.39,1720.56 1122.39,1720.96 1122.67,1720.96 1122.67,1720.56 1122.39,1720.56 "/>
<path clip-path="url(#clip322)" d="M1122.67 1720.96 L1122.67 1720.96 L1122.96 1720.96 L1122.96 1720.96 L1122.67 1720.96 L1122.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1122.67,1720.96 1122.67,1720.96 1122.96,1720.96 1122.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1122.96 1720.96 L1122.96 1720.96 L1123.24 1720.96 L1123.24 1720.96 L1122.96 1720.96 L1122.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1122.96,1720.96 1122.96,1720.96 1123.24,1720.96 1122.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1123.24 1720.76 L1123.24 1720.96 L1123.52 1720.96 L1123.52 1720.76 L1123.24 1720.76 L1123.24 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1123.24,1720.76 1123.24,1720.96 1123.52,1720.96 1123.52,1720.76 1123.24,1720.76 "/>
<path clip-path="url(#clip322)" d="M1123.52 1720.76 L1123.52 1720.96 L1123.8 1720.96 L1123.8 1720.76 L1123.52 1720.76 L1123.52 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1123.52,1720.76 1123.52,1720.96 1123.8,1720.96 1123.8,1720.76 1123.52,1720.76 "/>
<path clip-path="url(#clip322)" d="M1123.8 1720.96 L1123.8 1720.96 L1124.08 1720.96 L1124.08 1720.96 L1123.8 1720.96 L1123.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1123.8,1720.96 1123.8,1720.96 1124.08,1720.96 1123.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1124.08 1720.76 L1124.08 1720.96 L1124.36 1720.96 L1124.36 1720.76 L1124.08 1720.76 L1124.08 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1124.08,1720.76 1124.08,1720.96 1124.36,1720.96 1124.36,1720.76 1124.08,1720.76 "/>
<path clip-path="url(#clip322)" d="M1124.36 1720.76 L1124.36 1720.96 L1124.65 1720.96 L1124.65 1720.76 L1124.36 1720.76 L1124.36 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1124.36,1720.76 1124.36,1720.96 1124.65,1720.96 1124.65,1720.76 1124.36,1720.76 "/>
<path clip-path="url(#clip322)" d="M1124.65 1720.96 L1124.65 1720.96 L1124.93 1720.96 L1124.93 1720.96 L1124.65 1720.96 L1124.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1124.65,1720.96 1124.65,1720.96 1124.93,1720.96 1124.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1124.93 1720.96 L1124.93 1720.96 L1125.21 1720.96 L1125.21 1720.96 L1124.93 1720.96 L1124.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1124.93,1720.96 1124.93,1720.96 1125.21,1720.96 1124.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1125.21 1720.96 L1125.21 1720.96 L1125.49 1720.96 L1125.49 1720.96 L1125.21 1720.96 L1125.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1125.21,1720.96 1125.21,1720.96 1125.49,1720.96 1125.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1125.49 1720.96 L1125.49 1720.96 L1125.77 1720.96 L1125.77 1720.96 L1125.49 1720.96 L1125.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1125.49,1720.96 1125.49,1720.96 1125.77,1720.96 1125.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1125.77 1720.96 L1125.77 1720.96 L1126.06 1720.96 L1126.06 1720.96 L1125.77 1720.96 L1125.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1125.77,1720.96 1125.77,1720.96 1126.06,1720.96 1125.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1126.06 1720.96 L1126.06 1720.96 L1126.34 1720.96 L1126.34 1720.96 L1126.06 1720.96 L1126.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1126.06,1720.96 1126.06,1720.96 1126.34,1720.96 1126.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1126.34 1720.96 L1126.34 1720.96 L1126.62 1720.96 L1126.62 1720.96 L1126.34 1720.96 L1126.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1126.34,1720.96 1126.34,1720.96 1126.62,1720.96 1126.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1126.62 1720.96 L1126.62 1720.96 L1126.9 1720.96 L1126.9 1720.96 L1126.62 1720.96 L1126.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1126.62,1720.96 1126.62,1720.96 1126.9,1720.96 1126.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1126.9 1720.96 L1126.9 1720.96 L1127.18 1720.96 L1127.18 1720.96 L1126.9 1720.96 L1126.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1126.9,1720.96 1126.9,1720.96 1127.18,1720.96 1126.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1127.18 1720.96 L1127.18 1720.96 L1127.46 1720.96 L1127.46 1720.96 L1127.18 1720.96 L1127.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1127.18,1720.96 1127.18,1720.96 1127.46,1720.96 1127.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1127.46 1720.96 L1127.46 1720.96 L1127.75 1720.96 L1127.75 1720.96 L1127.46 1720.96 L1127.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1127.46,1720.96 1127.46,1720.96 1127.75,1720.96 1127.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1127.75 1720.96 L1127.75 1720.96 L1128.03 1720.96 L1128.03 1720.96 L1127.75 1720.96 L1127.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1127.75,1720.96 1127.75,1720.96 1128.03,1720.96 1127.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1128.03 1720.56 L1128.03 1720.96 L1128.31 1720.96 L1128.31 1720.56 L1128.03 1720.56 L1128.03 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1128.03,1720.56 1128.03,1720.96 1128.31,1720.96 1128.31,1720.56 1128.03,1720.56 "/>
<path clip-path="url(#clip322)" d="M1128.31 1720.96 L1128.31 1720.96 L1128.59 1720.96 L1128.59 1720.96 L1128.31 1720.96 L1128.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1128.31,1720.96 1128.31,1720.96 1128.59,1720.96 1128.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1128.59 1720.96 L1128.59 1720.96 L1128.87 1720.96 L1128.87 1720.96 L1128.59 1720.96 L1128.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1128.59,1720.96 1128.59,1720.96 1128.87,1720.96 1128.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1128.87 1720.96 L1128.87 1720.96 L1129.15 1720.96 L1129.15 1720.96 L1128.87 1720.96 L1128.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1128.87,1720.96 1128.87,1720.96 1129.15,1720.96 1128.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1129.15 1720.96 L1129.15 1720.96 L1129.44 1720.96 L1129.44 1720.96 L1129.15 1720.96 L1129.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1129.15,1720.96 1129.15,1720.96 1129.44,1720.96 1129.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1129.44 1720.96 L1129.44 1720.96 L1129.72 1720.96 L1129.72 1720.96 L1129.44 1720.96 L1129.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1129.44,1720.96 1129.44,1720.96 1129.72,1720.96 1129.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1129.72 1720.96 L1129.72 1720.96 L1130 1720.96 L1130 1720.96 L1129.72 1720.96 L1129.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1129.72,1720.96 1129.72,1720.96 1130,1720.96 1129.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1130 1720.96 L1130 1720.96 L1130.28 1720.96 L1130.28 1720.96 L1130 1720.96 L1130 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1130,1720.96 1130,1720.96 1130.28,1720.96 1130,1720.96 "/>
<path clip-path="url(#clip322)" d="M1130.28 1720.96 L1130.28 1720.96 L1130.56 1720.96 L1130.56 1720.96 L1130.28 1720.96 L1130.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1130.28,1720.96 1130.28,1720.96 1130.56,1720.96 1130.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1130.56 1720.76 L1130.56 1720.96 L1130.84 1720.96 L1130.84 1720.76 L1130.56 1720.76 L1130.56 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1130.56,1720.76 1130.56,1720.96 1130.84,1720.96 1130.84,1720.76 1130.56,1720.76 "/>
<path clip-path="url(#clip322)" d="M1130.84 1720.96 L1130.84 1720.96 L1131.13 1720.96 L1131.13 1720.96 L1130.84 1720.96 L1130.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1130.84,1720.96 1130.84,1720.96 1131.13,1720.96 1130.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1131.13 1720.96 L1131.13 1720.96 L1131.41 1720.96 L1131.41 1720.96 L1131.13 1720.96 L1131.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1131.13,1720.96 1131.13,1720.96 1131.41,1720.96 1131.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1131.41 1720.56 L1131.41 1720.96 L1131.69 1720.96 L1131.69 1720.56 L1131.41 1720.56 L1131.41 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1131.41,1720.56 1131.41,1720.96 1131.69,1720.96 1131.69,1720.56 1131.41,1720.56 "/>
<path clip-path="url(#clip322)" d="M1131.69 1720.96 L1131.69 1720.96 L1131.97 1720.96 L1131.97 1720.96 L1131.69 1720.96 L1131.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1131.69,1720.96 1131.69,1720.96 1131.97,1720.96 1131.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1131.97 1720.96 L1131.97 1720.96 L1132.25 1720.96 L1132.25 1720.96 L1131.97 1720.96 L1131.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1131.97,1720.96 1131.97,1720.96 1132.25,1720.96 1131.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1132.25 1720.96 L1132.25 1720.96 L1132.53 1720.96 L1132.53 1720.96 L1132.25 1720.96 L1132.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1132.25,1720.96 1132.25,1720.96 1132.53,1720.96 1132.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1132.53 1720.96 L1132.53 1720.96 L1132.82 1720.96 L1132.82 1720.96 L1132.53 1720.96 L1132.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1132.53,1720.96 1132.53,1720.96 1132.82,1720.96 1132.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1132.82 1720.96 L1132.82 1720.96 L1133.1 1720.96 L1133.1 1720.96 L1132.82 1720.96 L1132.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1132.82,1720.96 1132.82,1720.96 1133.1,1720.96 1132.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1133.1 1720.96 L1133.1 1720.96 L1133.38 1720.96 L1133.38 1720.96 L1133.1 1720.96 L1133.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1133.1,1720.96 1133.1,1720.96 1133.38,1720.96 1133.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1133.38 1720.96 L1133.38 1720.96 L1133.66 1720.96 L1133.66 1720.96 L1133.38 1720.96 L1133.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1133.38,1720.96 1133.38,1720.96 1133.66,1720.96 1133.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1133.66 1720.96 L1133.66 1720.96 L1133.94 1720.96 L1133.94 1720.96 L1133.66 1720.96 L1133.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1133.66,1720.96 1133.66,1720.96 1133.94,1720.96 1133.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1133.94 1720.96 L1133.94 1720.96 L1134.23 1720.96 L1134.23 1720.96 L1133.94 1720.96 L1133.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1133.94,1720.96 1133.94,1720.96 1134.23,1720.96 1133.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1134.23 1720.96 L1134.23 1720.96 L1134.51 1720.96 L1134.51 1720.96 L1134.23 1720.96 L1134.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1134.23,1720.96 1134.23,1720.96 1134.51,1720.96 1134.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1134.51 1720.96 L1134.51 1720.96 L1134.79 1720.96 L1134.79 1720.96 L1134.51 1720.96 L1134.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1134.51,1720.96 1134.51,1720.96 1134.79,1720.96 1134.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1134.79 1720.96 L1134.79 1720.96 L1135.07 1720.96 L1135.07 1720.96 L1134.79 1720.96 L1134.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1134.79,1720.96 1134.79,1720.96 1135.07,1720.96 1134.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1135.07 1720.96 L1135.07 1720.96 L1135.35 1720.96 L1135.35 1720.96 L1135.07 1720.96 L1135.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1135.07,1720.96 1135.07,1720.96 1135.35,1720.96 1135.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1135.35 1720.96 L1135.35 1720.96 L1135.63 1720.96 L1135.63 1720.96 L1135.35 1720.96 L1135.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1135.35,1720.96 1135.35,1720.96 1135.63,1720.96 1135.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1135.63 1720.96 L1135.63 1720.96 L1135.92 1720.96 L1135.92 1720.96 L1135.63 1720.96 L1135.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1135.63,1720.96 1135.63,1720.96 1135.92,1720.96 1135.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1135.92 1720.96 L1135.92 1720.96 L1136.2 1720.96 L1136.2 1720.96 L1135.92 1720.96 L1135.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1135.92,1720.96 1135.92,1720.96 1136.2,1720.96 1135.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1136.2 1720.96 L1136.2 1720.96 L1136.48 1720.96 L1136.48 1720.96 L1136.2 1720.96 L1136.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1136.2,1720.96 1136.2,1720.96 1136.48,1720.96 1136.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1136.48 1720.76 L1136.48 1720.96 L1136.76 1720.96 L1136.76 1720.76 L1136.48 1720.76 L1136.48 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1136.48,1720.76 1136.48,1720.96 1136.76,1720.96 1136.76,1720.76 1136.48,1720.76 "/>
<path clip-path="url(#clip322)" d="M1136.76 1720.96 L1136.76 1720.96 L1137.04 1720.96 L1137.04 1720.96 L1136.76 1720.96 L1136.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1136.76,1720.96 1136.76,1720.96 1137.04,1720.96 1136.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1137.04 1720.96 L1137.04 1720.96 L1137.32 1720.96 L1137.32 1720.96 L1137.04 1720.96 L1137.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1137.04,1720.96 1137.04,1720.96 1137.32,1720.96 1137.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1137.32 1720.96 L1137.32 1720.96 L1137.61 1720.96 L1137.61 1720.96 L1137.32 1720.96 L1137.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1137.32,1720.96 1137.32,1720.96 1137.61,1720.96 1137.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1137.61 1720.96 L1137.61 1720.96 L1137.89 1720.96 L1137.89 1720.96 L1137.61 1720.96 L1137.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1137.61,1720.96 1137.61,1720.96 1137.89,1720.96 1137.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1137.89 1720.76 L1137.89 1720.96 L1138.17 1720.96 L1138.17 1720.76 L1137.89 1720.76 L1137.89 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1137.89,1720.76 1137.89,1720.96 1138.17,1720.96 1138.17,1720.76 1137.89,1720.76 "/>
<path clip-path="url(#clip322)" d="M1138.17 1720.96 L1138.17 1720.96 L1138.45 1720.96 L1138.45 1720.96 L1138.17 1720.96 L1138.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1138.17,1720.96 1138.17,1720.96 1138.45,1720.96 1138.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1138.45 1720.76 L1138.45 1720.96 L1138.73 1720.96 L1138.73 1720.76 L1138.45 1720.76 L1138.45 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1138.45,1720.76 1138.45,1720.96 1138.73,1720.96 1138.73,1720.76 1138.45,1720.76 "/>
<path clip-path="url(#clip322)" d="M1138.73 1720.96 L1138.73 1720.96 L1139.01 1720.96 L1139.01 1720.96 L1138.73 1720.96 L1138.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1138.73,1720.96 1138.73,1720.96 1139.01,1720.96 1138.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1139.01 1720.96 L1139.01 1720.96 L1139.3 1720.96 L1139.3 1720.96 L1139.01 1720.96 L1139.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1139.01,1720.96 1139.01,1720.96 1139.3,1720.96 1139.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1139.3 1720.96 L1139.3 1720.96 L1139.58 1720.96 L1139.58 1720.96 L1139.3 1720.96 L1139.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1139.3,1720.96 1139.3,1720.96 1139.58,1720.96 1139.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1139.58 1720.56 L1139.58 1720.96 L1139.86 1720.96 L1139.86 1720.56 L1139.58 1720.56 L1139.58 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1139.58,1720.56 1139.58,1720.96 1139.86,1720.96 1139.86,1720.56 1139.58,1720.56 "/>
<path clip-path="url(#clip322)" d="M1139.86 1720.56 L1139.86 1720.96 L1140.14 1720.96 L1140.14 1720.56 L1139.86 1720.56 L1139.86 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1139.86,1720.56 1139.86,1720.96 1140.14,1720.96 1140.14,1720.56 1139.86,1720.56 "/>
<path clip-path="url(#clip322)" d="M1140.14 1720.96 L1140.14 1720.96 L1140.42 1720.96 L1140.42 1720.96 L1140.14 1720.96 L1140.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1140.14,1720.96 1140.14,1720.96 1140.42,1720.96 1140.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1140.42 1720.96 L1140.42 1720.96 L1140.7 1720.96 L1140.7 1720.96 L1140.42 1720.96 L1140.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1140.42,1720.96 1140.42,1720.96 1140.7,1720.96 1140.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1140.7 1720.56 L1140.7 1720.96 L1140.99 1720.96 L1140.99 1720.56 L1140.7 1720.56 L1140.7 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1140.7,1720.56 1140.7,1720.96 1140.99,1720.96 1140.99,1720.56 1140.7,1720.56 "/>
<path clip-path="url(#clip322)" d="M1140.99 1720.96 L1140.99 1720.96 L1141.27 1720.96 L1141.27 1720.96 L1140.99 1720.96 L1140.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1140.99,1720.96 1140.99,1720.96 1141.27,1720.96 1140.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1141.27 1720.96 L1141.27 1720.96 L1141.55 1720.96 L1141.55 1720.96 L1141.27 1720.96 L1141.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1141.27,1720.96 1141.27,1720.96 1141.55,1720.96 1141.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1141.55 1720.96 L1141.55 1720.96 L1141.83 1720.96 L1141.83 1720.96 L1141.55 1720.96 L1141.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1141.55,1720.96 1141.55,1720.96 1141.83,1720.96 1141.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1141.83 1720.96 L1141.83 1720.96 L1142.11 1720.96 L1142.11 1720.96 L1141.83 1720.96 L1141.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1141.83,1720.96 1141.83,1720.96 1142.11,1720.96 1141.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1142.11 1720.96 L1142.11 1720.96 L1142.4 1720.96 L1142.4 1720.96 L1142.11 1720.96 L1142.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1142.11,1720.96 1142.11,1720.96 1142.4,1720.96 1142.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1142.4 1720.96 L1142.4 1720.96 L1142.68 1720.96 L1142.68 1720.96 L1142.4 1720.96 L1142.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1142.4,1720.96 1142.4,1720.96 1142.68,1720.96 1142.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1142.68 1720.96 L1142.68 1720.96 L1142.96 1720.96 L1142.96 1720.96 L1142.68 1720.96 L1142.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1142.68,1720.96 1142.68,1720.96 1142.96,1720.96 1142.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1142.96 1720.96 L1142.96 1720.96 L1143.24 1720.96 L1143.24 1720.96 L1142.96 1720.96 L1142.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1142.96,1720.96 1142.96,1720.96 1143.24,1720.96 1142.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1143.24 1720.96 L1143.24 1720.96 L1143.52 1720.96 L1143.52 1720.96 L1143.24 1720.96 L1143.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1143.24,1720.96 1143.24,1720.96 1143.52,1720.96 1143.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1143.52 1720.96 L1143.52 1720.96 L1143.8 1720.96 L1143.8 1720.96 L1143.52 1720.96 L1143.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1143.52,1720.96 1143.52,1720.96 1143.8,1720.96 1143.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1143.8 1720.96 L1143.8 1720.96 L1144.09 1720.96 L1144.09 1720.96 L1143.8 1720.96 L1143.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1143.8,1720.96 1143.8,1720.96 1144.09,1720.96 1143.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1144.09 1720.96 L1144.09 1720.96 L1144.37 1720.96 L1144.37 1720.96 L1144.09 1720.96 L1144.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1144.09,1720.96 1144.09,1720.96 1144.37,1720.96 1144.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1144.37 1720.96 L1144.37 1720.96 L1144.65 1720.96 L1144.65 1720.96 L1144.37 1720.96 L1144.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1144.37,1720.96 1144.37,1720.96 1144.65,1720.96 1144.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1144.65 1720.96 L1144.65 1720.96 L1144.93 1720.96 L1144.93 1720.96 L1144.65 1720.96 L1144.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1144.65,1720.96 1144.65,1720.96 1144.93,1720.96 1144.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1144.93 1720.76 L1144.93 1720.96 L1145.21 1720.96 L1145.21 1720.76 L1144.93 1720.76 L1144.93 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1144.93,1720.76 1144.93,1720.96 1145.21,1720.96 1145.21,1720.76 1144.93,1720.76 "/>
<path clip-path="url(#clip322)" d="M1145.21 1720.96 L1145.21 1720.96 L1145.49 1720.96 L1145.49 1720.96 L1145.21 1720.96 L1145.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1145.21,1720.96 1145.21,1720.96 1145.49,1720.96 1145.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1145.49 1720.96 L1145.49 1720.96 L1145.78 1720.96 L1145.78 1720.96 L1145.49 1720.96 L1145.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1145.49,1720.96 1145.49,1720.96 1145.78,1720.96 1145.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1145.78 1720.96 L1145.78 1720.96 L1146.06 1720.96 L1146.06 1720.96 L1145.78 1720.96 L1145.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1145.78,1720.96 1145.78,1720.96 1146.06,1720.96 1145.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1146.06 1720.96 L1146.06 1720.96 L1146.34 1720.96 L1146.34 1720.96 L1146.06 1720.96 L1146.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1146.06,1720.96 1146.06,1720.96 1146.34,1720.96 1146.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1146.34 1720.96 L1146.34 1720.96 L1146.62 1720.96 L1146.62 1720.96 L1146.34 1720.96 L1146.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1146.34,1720.96 1146.34,1720.96 1146.62,1720.96 1146.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1146.62 1720.96 L1146.62 1720.96 L1146.9 1720.96 L1146.9 1720.96 L1146.62 1720.96 L1146.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1146.62,1720.96 1146.62,1720.96 1146.9,1720.96 1146.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1146.9 1720.96 L1146.9 1720.96 L1147.18 1720.96 L1147.18 1720.96 L1146.9 1720.96 L1146.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1146.9,1720.96 1146.9,1720.96 1147.18,1720.96 1146.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1147.18 1720.96 L1147.18 1720.96 L1147.47 1720.96 L1147.47 1720.96 L1147.18 1720.96 L1147.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1147.18,1720.96 1147.18,1720.96 1147.47,1720.96 1147.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1147.47 1720.76 L1147.47 1720.96 L1147.75 1720.96 L1147.75 1720.76 L1147.47 1720.76 L1147.47 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1147.47,1720.76 1147.47,1720.96 1147.75,1720.96 1147.75,1720.76 1147.47,1720.76 "/>
<path clip-path="url(#clip322)" d="M1147.75 1720.96 L1147.75 1720.96 L1148.03 1720.96 L1148.03 1720.96 L1147.75 1720.96 L1147.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1147.75,1720.96 1147.75,1720.96 1148.03,1720.96 1147.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1148.03 1720.96 L1148.03 1720.96 L1148.31 1720.96 L1148.31 1720.96 L1148.03 1720.96 L1148.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1148.03,1720.96 1148.03,1720.96 1148.31,1720.96 1148.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1148.31 1720.76 L1148.31 1720.96 L1148.59 1720.96 L1148.59 1720.76 L1148.31 1720.76 L1148.31 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1148.31,1720.76 1148.31,1720.96 1148.59,1720.96 1148.59,1720.76 1148.31,1720.76 "/>
<path clip-path="url(#clip322)" d="M1148.59 1720.96 L1148.59 1720.96 L1148.87 1720.96 L1148.87 1720.96 L1148.59 1720.96 L1148.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1148.59,1720.96 1148.59,1720.96 1148.87,1720.96 1148.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1148.87 1720.96 L1148.87 1720.96 L1149.16 1720.96 L1149.16 1720.96 L1148.87 1720.96 L1148.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1148.87,1720.96 1148.87,1720.96 1149.16,1720.96 1148.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1149.16 1720.96 L1149.16 1720.96 L1149.44 1720.96 L1149.44 1720.96 L1149.16 1720.96 L1149.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1149.16,1720.96 1149.16,1720.96 1149.44,1720.96 1149.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1149.44 1720.96 L1149.44 1720.96 L1149.72 1720.96 L1149.72 1720.96 L1149.44 1720.96 L1149.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1149.44,1720.96 1149.44,1720.96 1149.72,1720.96 1149.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1149.72 1720.76 L1149.72 1720.96 L1150 1720.96 L1150 1720.76 L1149.72 1720.76 L1149.72 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1149.72,1720.76 1149.72,1720.96 1150,1720.96 1150,1720.76 1149.72,1720.76 "/>
<path clip-path="url(#clip322)" d="M1150 1720.96 L1150 1720.96 L1150.28 1720.96 L1150.28 1720.96 L1150 1720.96 L1150 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1150,1720.96 1150,1720.96 1150.28,1720.96 1150,1720.96 "/>
<path clip-path="url(#clip322)" d="M1150.28 1720.96 L1150.28 1720.96 L1150.57 1720.96 L1150.57 1720.96 L1150.28 1720.96 L1150.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1150.28,1720.96 1150.28,1720.96 1150.57,1720.96 1150.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1150.57 1720.96 L1150.57 1720.96 L1150.85 1720.96 L1150.85 1720.96 L1150.57 1720.96 L1150.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1150.57,1720.96 1150.57,1720.96 1150.85,1720.96 1150.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1150.85 1720.96 L1150.85 1720.96 L1151.13 1720.96 L1151.13 1720.96 L1150.85 1720.96 L1150.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1150.85,1720.96 1150.85,1720.96 1151.13,1720.96 1150.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1151.13 1720.96 L1151.13 1720.96 L1151.41 1720.96 L1151.41 1720.96 L1151.13 1720.96 L1151.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1151.13,1720.96 1151.13,1720.96 1151.41,1720.96 1151.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1151.41 1720.96 L1151.41 1720.96 L1151.69 1720.96 L1151.69 1720.96 L1151.41 1720.96 L1151.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1151.41,1720.96 1151.41,1720.96 1151.69,1720.96 1151.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1151.69 1720.96 L1151.69 1720.96 L1151.97 1720.96 L1151.97 1720.96 L1151.69 1720.96 L1151.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1151.69,1720.96 1151.69,1720.96 1151.97,1720.96 1151.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1151.97 1720.96 L1151.97 1720.96 L1152.26 1720.96 L1152.26 1720.96 L1151.97 1720.96 L1151.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1151.97,1720.96 1151.97,1720.96 1152.26,1720.96 1151.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1152.26 1720.56 L1152.26 1720.96 L1152.54 1720.96 L1152.54 1720.56 L1152.26 1720.56 L1152.26 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1152.26,1720.56 1152.26,1720.96 1152.54,1720.96 1152.54,1720.56 1152.26,1720.56 "/>
<path clip-path="url(#clip322)" d="M1152.54 1720.96 L1152.54 1720.96 L1152.82 1720.96 L1152.82 1720.96 L1152.54 1720.96 L1152.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1152.54,1720.96 1152.54,1720.96 1152.82,1720.96 1152.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1152.82 1720.96 L1152.82 1720.96 L1153.1 1720.96 L1153.1 1720.96 L1152.82 1720.96 L1152.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1152.82,1720.96 1152.82,1720.96 1153.1,1720.96 1152.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1153.1 1720.96 L1153.1 1720.96 L1153.38 1720.96 L1153.38 1720.96 L1153.1 1720.96 L1153.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1153.1,1720.96 1153.1,1720.96 1153.38,1720.96 1153.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1153.38 1720.96 L1153.38 1720.96 L1153.66 1720.96 L1153.66 1720.96 L1153.38 1720.96 L1153.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1153.38,1720.96 1153.38,1720.96 1153.66,1720.96 1153.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1153.66 1720.76 L1153.66 1720.96 L1153.95 1720.96 L1153.95 1720.76 L1153.66 1720.76 L1153.66 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1153.66,1720.76 1153.66,1720.96 1153.95,1720.96 1153.95,1720.76 1153.66,1720.76 "/>
<path clip-path="url(#clip322)" d="M1153.95 1720.76 L1153.95 1720.96 L1154.23 1720.96 L1154.23 1720.76 L1153.95 1720.76 L1153.95 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1153.95,1720.76 1153.95,1720.96 1154.23,1720.96 1154.23,1720.76 1153.95,1720.76 "/>
<path clip-path="url(#clip322)" d="M1154.23 1720.96 L1154.23 1720.96 L1154.51 1720.96 L1154.51 1720.96 L1154.23 1720.96 L1154.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1154.23,1720.96 1154.23,1720.96 1154.51,1720.96 1154.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1154.51 1720.96 L1154.51 1720.96 L1154.79 1720.96 L1154.79 1720.96 L1154.51 1720.96 L1154.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1154.51,1720.96 1154.51,1720.96 1154.79,1720.96 1154.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1154.79 1720.96 L1154.79 1720.96 L1155.07 1720.96 L1155.07 1720.96 L1154.79 1720.96 L1154.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1154.79,1720.96 1154.79,1720.96 1155.07,1720.96 1154.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1155.07 1720.96 L1155.07 1720.96 L1155.35 1720.96 L1155.35 1720.96 L1155.07 1720.96 L1155.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1155.07,1720.96 1155.07,1720.96 1155.35,1720.96 1155.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1155.35 1720.96 L1155.35 1720.96 L1155.64 1720.96 L1155.64 1720.96 L1155.35 1720.96 L1155.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1155.35,1720.96 1155.35,1720.96 1155.64,1720.96 1155.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1155.64 1720.96 L1155.64 1720.96 L1155.92 1720.96 L1155.92 1720.96 L1155.64 1720.96 L1155.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1155.64,1720.96 1155.64,1720.96 1155.92,1720.96 1155.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1155.92 1720.76 L1155.92 1720.96 L1156.2 1720.96 L1156.2 1720.76 L1155.92 1720.76 L1155.92 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1155.92,1720.76 1155.92,1720.96 1156.2,1720.96 1156.2,1720.76 1155.92,1720.76 "/>
<path clip-path="url(#clip322)" d="M1156.2 1720.96 L1156.2 1720.96 L1156.48 1720.96 L1156.48 1720.96 L1156.2 1720.96 L1156.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1156.2,1720.96 1156.2,1720.96 1156.48,1720.96 1156.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1156.48 1720.96 L1156.48 1720.96 L1156.76 1720.96 L1156.76 1720.96 L1156.48 1720.96 L1156.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1156.48,1720.96 1156.48,1720.96 1156.76,1720.96 1156.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1156.76 1720.76 L1156.76 1720.96 L1157.04 1720.96 L1157.04 1720.76 L1156.76 1720.76 L1156.76 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1156.76,1720.76 1156.76,1720.96 1157.04,1720.96 1157.04,1720.76 1156.76,1720.76 "/>
<path clip-path="url(#clip322)" d="M1157.04 1720.96 L1157.04 1720.96 L1157.33 1720.96 L1157.33 1720.96 L1157.04 1720.96 L1157.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1157.04,1720.96 1157.04,1720.96 1157.33,1720.96 1157.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1157.33 1720.76 L1157.33 1720.96 L1157.61 1720.96 L1157.61 1720.76 L1157.33 1720.76 L1157.33 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1157.33,1720.76 1157.33,1720.96 1157.61,1720.96 1157.61,1720.76 1157.33,1720.76 "/>
<path clip-path="url(#clip322)" d="M1157.61 1720.96 L1157.61 1720.96 L1157.89 1720.96 L1157.89 1720.96 L1157.61 1720.96 L1157.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1157.61,1720.96 1157.61,1720.96 1157.89,1720.96 1157.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1157.89 1720.96 L1157.89 1720.96 L1158.17 1720.96 L1158.17 1720.96 L1157.89 1720.96 L1157.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1157.89,1720.96 1157.89,1720.96 1158.17,1720.96 1157.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1158.17 1720.96 L1158.17 1720.96 L1158.45 1720.96 L1158.45 1720.96 L1158.17 1720.96 L1158.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1158.17,1720.96 1158.17,1720.96 1158.45,1720.96 1158.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1158.45 1720.96 L1158.45 1720.96 L1158.74 1720.96 L1158.74 1720.96 L1158.45 1720.96 L1158.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1158.45,1720.96 1158.45,1720.96 1158.74,1720.96 1158.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1158.74 1720.96 L1158.74 1720.96 L1159.02 1720.96 L1159.02 1720.96 L1158.74 1720.96 L1158.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1158.74,1720.96 1158.74,1720.96 1159.02,1720.96 1158.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1159.02 1720.96 L1159.02 1720.96 L1159.3 1720.96 L1159.3 1720.96 L1159.02 1720.96 L1159.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1159.02,1720.96 1159.02,1720.96 1159.3,1720.96 1159.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1159.3 1720.76 L1159.3 1720.96 L1159.58 1720.96 L1159.58 1720.76 L1159.3 1720.76 L1159.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1159.3,1720.76 1159.3,1720.96 1159.58,1720.96 1159.58,1720.76 1159.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1159.58 1720.96 L1159.58 1720.96 L1159.86 1720.96 L1159.86 1720.96 L1159.58 1720.96 L1159.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1159.58,1720.96 1159.58,1720.96 1159.86,1720.96 1159.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1159.86 1720.76 L1159.86 1720.96 L1160.14 1720.96 L1160.14 1720.76 L1159.86 1720.76 L1159.86 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1159.86,1720.76 1159.86,1720.96 1160.14,1720.96 1160.14,1720.76 1159.86,1720.76 "/>
<path clip-path="url(#clip322)" d="M1160.14 1720.96 L1160.14 1720.96 L1160.43 1720.96 L1160.43 1720.96 L1160.14 1720.96 L1160.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1160.14,1720.96 1160.14,1720.96 1160.43,1720.96 1160.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1160.43 1720.76 L1160.43 1720.96 L1160.71 1720.96 L1160.71 1720.76 L1160.43 1720.76 L1160.43 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1160.43,1720.76 1160.43,1720.96 1160.71,1720.96 1160.71,1720.76 1160.43,1720.76 "/>
<path clip-path="url(#clip322)" d="M1160.71 1720.76 L1160.71 1720.96 L1160.99 1720.96 L1160.99 1720.76 L1160.71 1720.76 L1160.71 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1160.71,1720.76 1160.71,1720.96 1160.99,1720.96 1160.99,1720.76 1160.71,1720.76 "/>
<path clip-path="url(#clip322)" d="M1160.99 1720.96 L1160.99 1720.96 L1161.27 1720.96 L1161.27 1720.96 L1160.99 1720.96 L1160.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1160.99,1720.96 1160.99,1720.96 1161.27,1720.96 1160.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1161.27 1720.96 L1161.27 1720.96 L1161.55 1720.96 L1161.55 1720.96 L1161.27 1720.96 L1161.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1161.27,1720.96 1161.27,1720.96 1161.55,1720.96 1161.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1161.55 1720.96 L1161.55 1720.96 L1161.83 1720.96 L1161.83 1720.96 L1161.55 1720.96 L1161.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1161.55,1720.96 1161.55,1720.96 1161.83,1720.96 1161.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1161.83 1720.76 L1161.83 1720.96 L1162.12 1720.96 L1162.12 1720.76 L1161.83 1720.76 L1161.83 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1161.83,1720.76 1161.83,1720.96 1162.12,1720.96 1162.12,1720.76 1161.83,1720.76 "/>
<path clip-path="url(#clip322)" d="M1162.12 1720.96 L1162.12 1720.96 L1162.4 1720.96 L1162.4 1720.96 L1162.12 1720.96 L1162.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1162.12,1720.96 1162.12,1720.96 1162.4,1720.96 1162.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1162.4 1720.96 L1162.4 1720.96 L1162.68 1720.96 L1162.68 1720.96 L1162.4 1720.96 L1162.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1162.4,1720.96 1162.4,1720.96 1162.68,1720.96 1162.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1162.68 1720.96 L1162.68 1720.96 L1162.96 1720.96 L1162.96 1720.96 L1162.68 1720.96 L1162.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1162.68,1720.96 1162.68,1720.96 1162.96,1720.96 1162.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1162.96 1720.56 L1162.96 1720.96 L1163.24 1720.96 L1163.24 1720.56 L1162.96 1720.56 L1162.96 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1162.96,1720.56 1162.96,1720.96 1163.24,1720.96 1163.24,1720.56 1162.96,1720.56 "/>
<path clip-path="url(#clip322)" d="M1163.24 1720.76 L1163.24 1720.96 L1163.52 1720.96 L1163.52 1720.76 L1163.24 1720.76 L1163.24 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1163.24,1720.76 1163.24,1720.96 1163.52,1720.96 1163.52,1720.76 1163.24,1720.76 "/>
<path clip-path="url(#clip322)" d="M1163.52 1720.96 L1163.52 1720.96 L1163.81 1720.96 L1163.81 1720.96 L1163.52 1720.96 L1163.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1163.52,1720.96 1163.52,1720.96 1163.81,1720.96 1163.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1163.81 1720.96 L1163.81 1720.96 L1164.09 1720.96 L1164.09 1720.96 L1163.81 1720.96 L1163.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1163.81,1720.96 1163.81,1720.96 1164.09,1720.96 1163.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1164.09 1720.96 L1164.09 1720.96 L1164.37 1720.96 L1164.37 1720.96 L1164.09 1720.96 L1164.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1164.09,1720.96 1164.09,1720.96 1164.37,1720.96 1164.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1164.37 1720.96 L1164.37 1720.96 L1164.65 1720.96 L1164.65 1720.96 L1164.37 1720.96 L1164.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1164.37,1720.96 1164.37,1720.96 1164.65,1720.96 1164.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1164.65 1720.96 L1164.65 1720.96 L1164.93 1720.96 L1164.93 1720.96 L1164.65 1720.96 L1164.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1164.65,1720.96 1164.65,1720.96 1164.93,1720.96 1164.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1164.93 1720.96 L1164.93 1720.96 L1165.21 1720.96 L1165.21 1720.96 L1164.93 1720.96 L1164.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1164.93,1720.96 1164.93,1720.96 1165.21,1720.96 1164.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1165.21 1720.96 L1165.21 1720.96 L1165.5 1720.96 L1165.5 1720.96 L1165.21 1720.96 L1165.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1165.21,1720.96 1165.21,1720.96 1165.5,1720.96 1165.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1165.5 1720.76 L1165.5 1720.96 L1165.78 1720.96 L1165.78 1720.76 L1165.5 1720.76 L1165.5 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1165.5,1720.76 1165.5,1720.96 1165.78,1720.96 1165.78,1720.76 1165.5,1720.76 "/>
<path clip-path="url(#clip322)" d="M1165.78 1720.76 L1165.78 1720.96 L1166.06 1720.96 L1166.06 1720.76 L1165.78 1720.76 L1165.78 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1165.78,1720.76 1165.78,1720.96 1166.06,1720.96 1166.06,1720.76 1165.78,1720.76 "/>
<path clip-path="url(#clip322)" d="M1166.06 1720.76 L1166.06 1720.96 L1166.34 1720.96 L1166.34 1720.76 L1166.06 1720.76 L1166.06 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1166.06,1720.76 1166.06,1720.96 1166.34,1720.96 1166.34,1720.76 1166.06,1720.76 "/>
<path clip-path="url(#clip322)" d="M1166.34 1720.96 L1166.34 1720.96 L1166.62 1720.96 L1166.62 1720.96 L1166.34 1720.96 L1166.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1166.34,1720.96 1166.34,1720.96 1166.62,1720.96 1166.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1166.62 1720.96 L1166.62 1720.96 L1166.91 1720.96 L1166.91 1720.96 L1166.62 1720.96 L1166.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1166.62,1720.96 1166.62,1720.96 1166.91,1720.96 1166.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1166.91 1720.96 L1166.91 1720.96 L1167.19 1720.96 L1167.19 1720.96 L1166.91 1720.96 L1166.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1166.91,1720.96 1166.91,1720.96 1167.19,1720.96 1166.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1167.19 1720.96 L1167.19 1720.96 L1167.47 1720.96 L1167.47 1720.96 L1167.19 1720.96 L1167.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1167.19,1720.96 1167.19,1720.96 1167.47,1720.96 1167.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1167.47 1720.96 L1167.47 1720.96 L1167.75 1720.96 L1167.75 1720.96 L1167.47 1720.96 L1167.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1167.47,1720.96 1167.47,1720.96 1167.75,1720.96 1167.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1167.75 1720.76 L1167.75 1720.96 L1168.03 1720.96 L1168.03 1720.76 L1167.75 1720.76 L1167.75 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1167.75,1720.76 1167.75,1720.96 1168.03,1720.96 1168.03,1720.76 1167.75,1720.76 "/>
<path clip-path="url(#clip322)" d="M1168.03 1720.76 L1168.03 1720.96 L1168.31 1720.96 L1168.31 1720.76 L1168.03 1720.76 L1168.03 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1168.03,1720.76 1168.03,1720.96 1168.31,1720.96 1168.31,1720.76 1168.03,1720.76 "/>
<path clip-path="url(#clip322)" d="M1168.31 1720.76 L1168.31 1720.96 L1168.6 1720.96 L1168.6 1720.76 L1168.31 1720.76 L1168.31 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1168.31,1720.76 1168.31,1720.96 1168.6,1720.96 1168.6,1720.76 1168.31,1720.76 "/>
<path clip-path="url(#clip322)" d="M1168.6 1720.96 L1168.6 1720.96 L1168.88 1720.96 L1168.88 1720.96 L1168.6 1720.96 L1168.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1168.6,1720.96 1168.6,1720.96 1168.88,1720.96 1168.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1168.88 1720.96 L1168.88 1720.96 L1169.16 1720.96 L1169.16 1720.96 L1168.88 1720.96 L1168.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1168.88,1720.96 1168.88,1720.96 1169.16,1720.96 1168.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1169.16 1720.96 L1169.16 1720.96 L1169.44 1720.96 L1169.44 1720.96 L1169.16 1720.96 L1169.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1169.16,1720.96 1169.16,1720.96 1169.44,1720.96 1169.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1169.44 1720.96 L1169.44 1720.96 L1169.72 1720.96 L1169.72 1720.96 L1169.44 1720.96 L1169.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1169.44,1720.96 1169.44,1720.96 1169.72,1720.96 1169.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1169.72 1720.96 L1169.72 1720.96 L1170 1720.96 L1170 1720.96 L1169.72 1720.96 L1169.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1169.72,1720.96 1169.72,1720.96 1170,1720.96 1169.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1170 1720.96 L1170 1720.96 L1170.29 1720.96 L1170.29 1720.96 L1170 1720.96 L1170 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1170,1720.96 1170,1720.96 1170.29,1720.96 1170,1720.96 "/>
<path clip-path="url(#clip322)" d="M1170.29 1720.76 L1170.29 1720.96 L1170.57 1720.96 L1170.57 1720.76 L1170.29 1720.76 L1170.29 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1170.29,1720.76 1170.29,1720.96 1170.57,1720.96 1170.57,1720.76 1170.29,1720.76 "/>
<path clip-path="url(#clip322)" d="M1170.57 1720.96 L1170.57 1720.96 L1170.85 1720.96 L1170.85 1720.96 L1170.57 1720.96 L1170.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1170.57,1720.96 1170.57,1720.96 1170.85,1720.96 1170.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1170.85 1720.96 L1170.85 1720.96 L1171.13 1720.96 L1171.13 1720.96 L1170.85 1720.96 L1170.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1170.85,1720.96 1170.85,1720.96 1171.13,1720.96 1170.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1171.13 1720.96 L1171.13 1720.96 L1171.41 1720.96 L1171.41 1720.96 L1171.13 1720.96 L1171.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1171.13,1720.96 1171.13,1720.96 1171.41,1720.96 1171.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1171.41 1720.96 L1171.41 1720.96 L1171.69 1720.96 L1171.69 1720.96 L1171.41 1720.96 L1171.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1171.41,1720.96 1171.41,1720.96 1171.69,1720.96 1171.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1171.69 1720.56 L1171.69 1720.96 L1171.98 1720.96 L1171.98 1720.56 L1171.69 1720.56 L1171.69 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1171.69,1720.56 1171.69,1720.96 1171.98,1720.96 1171.98,1720.56 1171.69,1720.56 "/>
<path clip-path="url(#clip322)" d="M1171.98 1720.96 L1171.98 1720.96 L1172.26 1720.96 L1172.26 1720.96 L1171.98 1720.96 L1171.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1171.98,1720.96 1171.98,1720.96 1172.26,1720.96 1171.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1172.26 1720.96 L1172.26 1720.96 L1172.54 1720.96 L1172.54 1720.96 L1172.26 1720.96 L1172.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1172.26,1720.96 1172.26,1720.96 1172.54,1720.96 1172.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1172.54 1720.96 L1172.54 1720.96 L1172.82 1720.96 L1172.82 1720.96 L1172.54 1720.96 L1172.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1172.54,1720.96 1172.54,1720.96 1172.82,1720.96 1172.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1172.82 1720.76 L1172.82 1720.96 L1173.1 1720.96 L1173.1 1720.76 L1172.82 1720.76 L1172.82 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1172.82,1720.76 1172.82,1720.96 1173.1,1720.96 1173.1,1720.76 1172.82,1720.76 "/>
<path clip-path="url(#clip322)" d="M1173.1 1720.96 L1173.1 1720.96 L1173.38 1720.96 L1173.38 1720.96 L1173.1 1720.96 L1173.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1173.1,1720.96 1173.1,1720.96 1173.38,1720.96 1173.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1173.38 1720.96 L1173.38 1720.96 L1173.67 1720.96 L1173.67 1720.96 L1173.38 1720.96 L1173.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1173.38,1720.96 1173.38,1720.96 1173.67,1720.96 1173.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1173.67 1720.96 L1173.67 1720.96 L1173.95 1720.96 L1173.95 1720.96 L1173.67 1720.96 L1173.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1173.67,1720.96 1173.67,1720.96 1173.95,1720.96 1173.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1173.95 1720.96 L1173.95 1720.96 L1174.23 1720.96 L1174.23 1720.96 L1173.95 1720.96 L1173.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1173.95,1720.96 1173.95,1720.96 1174.23,1720.96 1173.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1174.23 1720.96 L1174.23 1720.96 L1174.51 1720.96 L1174.51 1720.96 L1174.23 1720.96 L1174.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1174.23,1720.96 1174.23,1720.96 1174.51,1720.96 1174.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1174.51 1720.96 L1174.51 1720.96 L1174.79 1720.96 L1174.79 1720.96 L1174.51 1720.96 L1174.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1174.51,1720.96 1174.51,1720.96 1174.79,1720.96 1174.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1174.79 1720.96 L1174.79 1720.96 L1175.08 1720.96 L1175.08 1720.96 L1174.79 1720.96 L1174.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1174.79,1720.96 1174.79,1720.96 1175.08,1720.96 1174.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1175.08 1720.76 L1175.08 1720.96 L1175.36 1720.96 L1175.36 1720.76 L1175.08 1720.76 L1175.08 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1175.08,1720.76 1175.08,1720.96 1175.36,1720.96 1175.36,1720.76 1175.08,1720.76 "/>
<path clip-path="url(#clip322)" d="M1175.36 1720.96 L1175.36 1720.96 L1175.64 1720.96 L1175.64 1720.96 L1175.36 1720.96 L1175.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1175.36,1720.96 1175.36,1720.96 1175.64,1720.96 1175.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1175.64 1720.96 L1175.64 1720.96 L1175.92 1720.96 L1175.92 1720.96 L1175.64 1720.96 L1175.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1175.64,1720.96 1175.64,1720.96 1175.92,1720.96 1175.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1175.92 1720.96 L1175.92 1720.96 L1176.2 1720.96 L1176.2 1720.96 L1175.92 1720.96 L1175.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1175.92,1720.96 1175.92,1720.96 1176.2,1720.96 1175.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1176.2 1720.96 L1176.2 1720.96 L1176.48 1720.96 L1176.48 1720.96 L1176.2 1720.96 L1176.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1176.2,1720.96 1176.2,1720.96 1176.48,1720.96 1176.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1176.48 1720.76 L1176.48 1720.96 L1176.77 1720.96 L1176.77 1720.76 L1176.48 1720.76 L1176.48 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1176.48,1720.76 1176.48,1720.96 1176.77,1720.96 1176.77,1720.76 1176.48,1720.76 "/>
<path clip-path="url(#clip322)" d="M1176.77 1720.76 L1176.77 1720.96 L1177.05 1720.96 L1177.05 1720.76 L1176.77 1720.76 L1176.77 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1176.77,1720.76 1176.77,1720.96 1177.05,1720.96 1177.05,1720.76 1176.77,1720.76 "/>
<path clip-path="url(#clip322)" d="M1177.05 1720.96 L1177.05 1720.96 L1177.33 1720.96 L1177.33 1720.96 L1177.05 1720.96 L1177.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1177.05,1720.96 1177.05,1720.96 1177.33,1720.96 1177.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1177.33 1720.76 L1177.33 1720.96 L1177.61 1720.96 L1177.61 1720.76 L1177.33 1720.76 L1177.33 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1177.33,1720.76 1177.33,1720.96 1177.61,1720.96 1177.61,1720.76 1177.33,1720.76 "/>
<path clip-path="url(#clip322)" d="M1177.61 1720.96 L1177.61 1720.96 L1177.89 1720.96 L1177.89 1720.96 L1177.61 1720.96 L1177.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1177.61,1720.96 1177.61,1720.96 1177.89,1720.96 1177.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1177.89 1720.96 L1177.89 1720.96 L1178.17 1720.96 L1178.17 1720.96 L1177.89 1720.96 L1177.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1177.89,1720.96 1177.89,1720.96 1178.17,1720.96 1177.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1178.17 1720.96 L1178.17 1720.96 L1178.46 1720.96 L1178.46 1720.96 L1178.17 1720.96 L1178.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1178.17,1720.96 1178.17,1720.96 1178.46,1720.96 1178.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1178.46 1720.96 L1178.46 1720.96 L1178.74 1720.96 L1178.74 1720.96 L1178.46 1720.96 L1178.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1178.46,1720.96 1178.46,1720.96 1178.74,1720.96 1178.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1178.74 1720.96 L1178.74 1720.96 L1179.02 1720.96 L1179.02 1720.96 L1178.74 1720.96 L1178.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1178.74,1720.96 1178.74,1720.96 1179.02,1720.96 1178.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1179.02 1720.96 L1179.02 1720.96 L1179.3 1720.96 L1179.3 1720.96 L1179.02 1720.96 L1179.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1179.02,1720.96 1179.02,1720.96 1179.3,1720.96 1179.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1179.3 1720.96 L1179.3 1720.96 L1179.58 1720.96 L1179.58 1720.96 L1179.3 1720.96 L1179.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1179.3,1720.96 1179.3,1720.96 1179.58,1720.96 1179.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1179.58 1720.96 L1179.58 1720.96 L1179.86 1720.96 L1179.86 1720.96 L1179.58 1720.96 L1179.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1179.58,1720.96 1179.58,1720.96 1179.86,1720.96 1179.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1179.86 1720.96 L1179.86 1720.96 L1180.15 1720.96 L1180.15 1720.96 L1179.86 1720.96 L1179.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1179.86,1720.96 1179.86,1720.96 1180.15,1720.96 1179.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1180.15 1720.96 L1180.15 1720.96 L1180.43 1720.96 L1180.43 1720.96 L1180.15 1720.96 L1180.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1180.15,1720.96 1180.15,1720.96 1180.43,1720.96 1180.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1180.43 1720.96 L1180.43 1720.96 L1180.71 1720.96 L1180.71 1720.96 L1180.43 1720.96 L1180.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1180.43,1720.96 1180.43,1720.96 1180.71,1720.96 1180.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1180.71 1720.76 L1180.71 1720.96 L1180.99 1720.96 L1180.99 1720.76 L1180.71 1720.76 L1180.71 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1180.71,1720.76 1180.71,1720.96 1180.99,1720.96 1180.99,1720.76 1180.71,1720.76 "/>
<path clip-path="url(#clip322)" d="M1180.99 1720.96 L1180.99 1720.96 L1181.27 1720.96 L1181.27 1720.96 L1180.99 1720.96 L1180.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1180.99,1720.96 1180.99,1720.96 1181.27,1720.96 1180.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1181.27 1720.96 L1181.27 1720.96 L1181.55 1720.96 L1181.55 1720.96 L1181.27 1720.96 L1181.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1181.27,1720.96 1181.27,1720.96 1181.55,1720.96 1181.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1181.55 1720.96 L1181.55 1720.96 L1181.84 1720.96 L1181.84 1720.96 L1181.55 1720.96 L1181.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1181.55,1720.96 1181.55,1720.96 1181.84,1720.96 1181.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1181.84 1720.76 L1181.84 1720.96 L1182.12 1720.96 L1182.12 1720.76 L1181.84 1720.76 L1181.84 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1181.84,1720.76 1181.84,1720.96 1182.12,1720.96 1182.12,1720.76 1181.84,1720.76 "/>
<path clip-path="url(#clip322)" d="M1182.12 1720.96 L1182.12 1720.96 L1182.4 1720.96 L1182.4 1720.96 L1182.12 1720.96 L1182.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1182.12,1720.96 1182.12,1720.96 1182.4,1720.96 1182.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1182.4 1720.96 L1182.4 1720.96 L1182.68 1720.96 L1182.68 1720.96 L1182.4 1720.96 L1182.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1182.4,1720.96 1182.4,1720.96 1182.68,1720.96 1182.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1182.68 1720.96 L1182.68 1720.96 L1182.96 1720.96 L1182.96 1720.96 L1182.68 1720.96 L1182.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1182.68,1720.96 1182.68,1720.96 1182.96,1720.96 1182.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1182.96 1720.96 L1182.96 1720.96 L1183.25 1720.96 L1183.25 1720.96 L1182.96 1720.96 L1182.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1182.96,1720.96 1182.96,1720.96 1183.25,1720.96 1182.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1183.25 1720.96 L1183.25 1720.96 L1183.53 1720.96 L1183.53 1720.96 L1183.25 1720.96 L1183.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1183.25,1720.96 1183.25,1720.96 1183.53,1720.96 1183.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1183.53 1720.96 L1183.53 1720.96 L1183.81 1720.96 L1183.81 1720.96 L1183.53 1720.96 L1183.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1183.53,1720.96 1183.53,1720.96 1183.81,1720.96 1183.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1183.81 1720.96 L1183.81 1720.96 L1184.09 1720.96 L1184.09 1720.96 L1183.81 1720.96 L1183.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1183.81,1720.96 1183.81,1720.96 1184.09,1720.96 1183.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1184.09 1720.96 L1184.09 1720.96 L1184.37 1720.96 L1184.37 1720.96 L1184.09 1720.96 L1184.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1184.09,1720.96 1184.09,1720.96 1184.37,1720.96 1184.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1184.37 1720.96 L1184.37 1720.96 L1184.65 1720.96 L1184.65 1720.96 L1184.37 1720.96 L1184.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1184.37,1720.96 1184.37,1720.96 1184.65,1720.96 1184.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1184.65 1720.76 L1184.65 1720.96 L1184.94 1720.96 L1184.94 1720.76 L1184.65 1720.76 L1184.65 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1184.65,1720.76 1184.65,1720.96 1184.94,1720.96 1184.94,1720.76 1184.65,1720.76 "/>
<path clip-path="url(#clip322)" d="M1184.94 1720.96 L1184.94 1720.96 L1185.22 1720.96 L1185.22 1720.96 L1184.94 1720.96 L1184.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1184.94,1720.96 1184.94,1720.96 1185.22,1720.96 1184.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1185.22 1720.96 L1185.22 1720.96 L1185.5 1720.96 L1185.5 1720.96 L1185.22 1720.96 L1185.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1185.22,1720.96 1185.22,1720.96 1185.5,1720.96 1185.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1185.5 1720.96 L1185.5 1720.96 L1185.78 1720.96 L1185.78 1720.96 L1185.5 1720.96 L1185.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1185.5,1720.96 1185.5,1720.96 1185.78,1720.96 1185.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1185.78 1720.76 L1185.78 1720.96 L1186.06 1720.96 L1186.06 1720.76 L1185.78 1720.76 L1185.78 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1185.78,1720.76 1185.78,1720.96 1186.06,1720.96 1186.06,1720.76 1185.78,1720.76 "/>
<path clip-path="url(#clip322)" d="M1186.06 1720.96 L1186.06 1720.96 L1186.34 1720.96 L1186.34 1720.96 L1186.06 1720.96 L1186.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1186.06,1720.96 1186.06,1720.96 1186.34,1720.96 1186.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1186.34 1720.96 L1186.34 1720.96 L1186.63 1720.96 L1186.63 1720.96 L1186.34 1720.96 L1186.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1186.34,1720.96 1186.34,1720.96 1186.63,1720.96 1186.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1186.63 1720.96 L1186.63 1720.96 L1186.91 1720.96 L1186.91 1720.96 L1186.63 1720.96 L1186.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1186.63,1720.96 1186.63,1720.96 1186.91,1720.96 1186.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1186.91 1720.96 L1186.91 1720.96 L1187.19 1720.96 L1187.19 1720.96 L1186.91 1720.96 L1186.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1186.91,1720.96 1186.91,1720.96 1187.19,1720.96 1186.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1187.19 1720.96 L1187.19 1720.96 L1187.47 1720.96 L1187.47 1720.96 L1187.19 1720.96 L1187.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1187.19,1720.96 1187.19,1720.96 1187.47,1720.96 1187.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1187.47 1720.96 L1187.47 1720.96 L1187.75 1720.96 L1187.75 1720.96 L1187.47 1720.96 L1187.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1187.47,1720.96 1187.47,1720.96 1187.75,1720.96 1187.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1187.75 1720.96 L1187.75 1720.96 L1188.03 1720.96 L1188.03 1720.96 L1187.75 1720.96 L1187.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1187.75,1720.96 1187.75,1720.96 1188.03,1720.96 1187.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1188.03 1720.96 L1188.03 1720.96 L1188.32 1720.96 L1188.32 1720.96 L1188.03 1720.96 L1188.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1188.03,1720.96 1188.03,1720.96 1188.32,1720.96 1188.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1188.32 1720.96 L1188.32 1720.96 L1188.6 1720.96 L1188.6 1720.96 L1188.32 1720.96 L1188.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1188.32,1720.96 1188.32,1720.96 1188.6,1720.96 1188.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1188.6 1720.96 L1188.6 1720.96 L1188.88 1720.96 L1188.88 1720.96 L1188.6 1720.96 L1188.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1188.6,1720.96 1188.6,1720.96 1188.88,1720.96 1188.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1188.88 1720.96 L1188.88 1720.96 L1189.16 1720.96 L1189.16 1720.96 L1188.88 1720.96 L1188.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1188.88,1720.96 1188.88,1720.96 1189.16,1720.96 1188.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1189.16 1720.96 L1189.16 1720.96 L1189.44 1720.96 L1189.44 1720.96 L1189.16 1720.96 L1189.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1189.16,1720.96 1189.16,1720.96 1189.44,1720.96 1189.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1189.44 1720.96 L1189.44 1720.96 L1189.73 1720.96 L1189.73 1720.96 L1189.44 1720.96 L1189.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1189.44,1720.96 1189.44,1720.96 1189.73,1720.96 1189.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1189.73 1720.96 L1189.73 1720.96 L1190.01 1720.96 L1190.01 1720.96 L1189.73 1720.96 L1189.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1189.73,1720.96 1189.73,1720.96 1190.01,1720.96 1189.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1190.01 1720.96 L1190.01 1720.96 L1190.29 1720.96 L1190.29 1720.96 L1190.01 1720.96 L1190.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1190.01,1720.96 1190.01,1720.96 1190.29,1720.96 1190.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1190.29 1720.96 L1190.29 1720.96 L1190.57 1720.96 L1190.57 1720.96 L1190.29 1720.96 L1190.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1190.29,1720.96 1190.29,1720.96 1190.57,1720.96 1190.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1190.57 1720.96 L1190.57 1720.96 L1190.85 1720.96 L1190.85 1720.96 L1190.57 1720.96 L1190.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1190.57,1720.96 1190.57,1720.96 1190.85,1720.96 1190.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1190.85 1720.96 L1190.85 1720.96 L1191.13 1720.96 L1191.13 1720.96 L1190.85 1720.96 L1190.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1190.85,1720.96 1190.85,1720.96 1191.13,1720.96 1190.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1191.13 1720.76 L1191.13 1720.96 L1191.42 1720.96 L1191.42 1720.76 L1191.13 1720.76 L1191.13 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1191.13,1720.76 1191.13,1720.96 1191.42,1720.96 1191.42,1720.76 1191.13,1720.76 "/>
<path clip-path="url(#clip322)" d="M1191.42 1720.96 L1191.42 1720.96 L1191.7 1720.96 L1191.7 1720.96 L1191.42 1720.96 L1191.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1191.42,1720.96 1191.42,1720.96 1191.7,1720.96 1191.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1191.7 1720.76 L1191.7 1720.96 L1191.98 1720.96 L1191.98 1720.76 L1191.7 1720.76 L1191.7 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1191.7,1720.76 1191.7,1720.96 1191.98,1720.96 1191.98,1720.76 1191.7,1720.76 "/>
<path clip-path="url(#clip322)" d="M1191.98 1720.96 L1191.98 1720.96 L1192.26 1720.96 L1192.26 1720.96 L1191.98 1720.96 L1191.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1191.98,1720.96 1191.98,1720.96 1192.26,1720.96 1191.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1192.26 1720.96 L1192.26 1720.96 L1192.54 1720.96 L1192.54 1720.96 L1192.26 1720.96 L1192.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1192.26,1720.96 1192.26,1720.96 1192.54,1720.96 1192.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1192.54 1720.76 L1192.54 1720.96 L1192.82 1720.96 L1192.82 1720.76 L1192.54 1720.76 L1192.54 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1192.54,1720.76 1192.54,1720.96 1192.82,1720.96 1192.82,1720.76 1192.54,1720.76 "/>
<path clip-path="url(#clip322)" d="M1192.82 1720.96 L1192.82 1720.96 L1193.11 1720.96 L1193.11 1720.96 L1192.82 1720.96 L1192.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1192.82,1720.96 1192.82,1720.96 1193.11,1720.96 1192.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1193.11 1720.96 L1193.11 1720.96 L1193.39 1720.96 L1193.39 1720.96 L1193.11 1720.96 L1193.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1193.11,1720.96 1193.11,1720.96 1193.39,1720.96 1193.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1193.39 1720.76 L1193.39 1720.96 L1193.67 1720.96 L1193.67 1720.76 L1193.39 1720.76 L1193.39 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1193.39,1720.76 1193.39,1720.96 1193.67,1720.96 1193.67,1720.76 1193.39,1720.76 "/>
<path clip-path="url(#clip322)" d="M1193.67 1720.96 L1193.67 1720.96 L1193.95 1720.96 L1193.95 1720.96 L1193.67 1720.96 L1193.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1193.67,1720.96 1193.67,1720.96 1193.95,1720.96 1193.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1193.95 1720.96 L1193.95 1720.96 L1194.23 1720.96 L1194.23 1720.96 L1193.95 1720.96 L1193.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1193.95,1720.96 1193.95,1720.96 1194.23,1720.96 1193.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1194.23 1720.96 L1194.23 1720.96 L1194.51 1720.96 L1194.51 1720.96 L1194.23 1720.96 L1194.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1194.23,1720.96 1194.23,1720.96 1194.51,1720.96 1194.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1194.51 1720.96 L1194.51 1720.96 L1194.8 1720.96 L1194.8 1720.96 L1194.51 1720.96 L1194.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1194.51,1720.96 1194.51,1720.96 1194.8,1720.96 1194.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1194.8 1720.96 L1194.8 1720.96 L1195.08 1720.96 L1195.08 1720.96 L1194.8 1720.96 L1194.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1194.8,1720.96 1194.8,1720.96 1195.08,1720.96 1194.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1195.08 1720.96 L1195.08 1720.96 L1195.36 1720.96 L1195.36 1720.96 L1195.08 1720.96 L1195.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1195.08,1720.96 1195.08,1720.96 1195.36,1720.96 1195.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1195.36 1720.96 L1195.36 1720.96 L1195.64 1720.96 L1195.64 1720.96 L1195.36 1720.96 L1195.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1195.36,1720.96 1195.36,1720.96 1195.64,1720.96 1195.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1195.64 1720.76 L1195.64 1720.96 L1195.92 1720.96 L1195.92 1720.76 L1195.64 1720.76 L1195.64 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1195.64,1720.76 1195.64,1720.96 1195.92,1720.96 1195.92,1720.76 1195.64,1720.76 "/>
<path clip-path="url(#clip322)" d="M1195.92 1720.96 L1195.92 1720.96 L1196.2 1720.96 L1196.2 1720.96 L1195.92 1720.96 L1195.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1195.92,1720.96 1195.92,1720.96 1196.2,1720.96 1195.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1196.2 1720.96 L1196.2 1720.96 L1196.49 1720.96 L1196.49 1720.96 L1196.2 1720.96 L1196.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1196.2,1720.96 1196.2,1720.96 1196.49,1720.96 1196.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1196.49 1720.96 L1196.49 1720.96 L1196.77 1720.96 L1196.77 1720.96 L1196.49 1720.96 L1196.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1196.49,1720.96 1196.49,1720.96 1196.77,1720.96 1196.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1196.77 1720.96 L1196.77 1720.96 L1197.05 1720.96 L1197.05 1720.96 L1196.77 1720.96 L1196.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1196.77,1720.96 1196.77,1720.96 1197.05,1720.96 1196.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1197.05 1720.96 L1197.05 1720.96 L1197.33 1720.96 L1197.33 1720.96 L1197.05 1720.96 L1197.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1197.05,1720.96 1197.05,1720.96 1197.33,1720.96 1197.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1197.33 1720.96 L1197.33 1720.96 L1197.61 1720.96 L1197.61 1720.96 L1197.33 1720.96 L1197.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1197.33,1720.96 1197.33,1720.96 1197.61,1720.96 1197.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1197.61 1720.96 L1197.61 1720.96 L1197.9 1720.96 L1197.9 1720.96 L1197.61 1720.96 L1197.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1197.61,1720.96 1197.61,1720.96 1197.9,1720.96 1197.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1197.9 1720.96 L1197.9 1720.96 L1198.18 1720.96 L1198.18 1720.96 L1197.9 1720.96 L1197.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1197.9,1720.96 1197.9,1720.96 1198.18,1720.96 1197.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1198.18 1720.76 L1198.18 1720.96 L1198.46 1720.96 L1198.46 1720.76 L1198.18 1720.76 L1198.18 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1198.18,1720.76 1198.18,1720.96 1198.46,1720.96 1198.46,1720.76 1198.18,1720.76 "/>
<path clip-path="url(#clip322)" d="M1198.46 1720.96 L1198.46 1720.96 L1198.74 1720.96 L1198.74 1720.96 L1198.46 1720.96 L1198.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1198.46,1720.96 1198.46,1720.96 1198.74,1720.96 1198.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1198.74 1720.96 L1198.74 1720.96 L1199.02 1720.96 L1199.02 1720.96 L1198.74 1720.96 L1198.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1198.74,1720.96 1198.74,1720.96 1199.02,1720.96 1198.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1199.02 1720.76 L1199.02 1720.96 L1199.3 1720.96 L1199.3 1720.76 L1199.02 1720.76 L1199.02 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1199.02,1720.76 1199.02,1720.96 1199.3,1720.96 1199.3,1720.76 1199.02,1720.76 "/>
<path clip-path="url(#clip322)" d="M1199.3 1720.96 L1199.3 1720.96 L1199.59 1720.96 L1199.59 1720.96 L1199.3 1720.96 L1199.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1199.3,1720.96 1199.3,1720.96 1199.59,1720.96 1199.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1199.59 1720.96 L1199.59 1720.96 L1199.87 1720.96 L1199.87 1720.96 L1199.59 1720.96 L1199.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1199.59,1720.96 1199.59,1720.96 1199.87,1720.96 1199.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1199.87 1720.96 L1199.87 1720.96 L1200.15 1720.96 L1200.15 1720.96 L1199.87 1720.96 L1199.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1199.87,1720.96 1199.87,1720.96 1200.15,1720.96 1199.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1200.15 1720.96 L1200.15 1720.96 L1200.43 1720.96 L1200.43 1720.96 L1200.15 1720.96 L1200.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1200.15,1720.96 1200.15,1720.96 1200.43,1720.96 1200.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1200.43 1720.96 L1200.43 1720.96 L1200.71 1720.96 L1200.71 1720.96 L1200.43 1720.96 L1200.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1200.43,1720.96 1200.43,1720.96 1200.71,1720.96 1200.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1200.71 1720.96 L1200.71 1720.96 L1200.99 1720.96 L1200.99 1720.96 L1200.71 1720.96 L1200.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1200.71,1720.96 1200.71,1720.96 1200.99,1720.96 1200.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1200.99 1720.96 L1200.99 1720.96 L1201.28 1720.96 L1201.28 1720.96 L1200.99 1720.96 L1200.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1200.99,1720.96 1200.99,1720.96 1201.28,1720.96 1200.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1201.28 1720.76 L1201.28 1720.96 L1201.56 1720.96 L1201.56 1720.76 L1201.28 1720.76 L1201.28 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1201.28,1720.76 1201.28,1720.96 1201.56,1720.96 1201.56,1720.76 1201.28,1720.76 "/>
<path clip-path="url(#clip322)" d="M1201.56 1720.96 L1201.56 1720.96 L1201.84 1720.96 L1201.84 1720.96 L1201.56 1720.96 L1201.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1201.56,1720.96 1201.56,1720.96 1201.84,1720.96 1201.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1201.84 1720.96 L1201.84 1720.96 L1202.12 1720.96 L1202.12 1720.96 L1201.84 1720.96 L1201.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1201.84,1720.96 1201.84,1720.96 1202.12,1720.96 1201.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1202.12 1720.96 L1202.12 1720.96 L1202.4 1720.96 L1202.4 1720.96 L1202.12 1720.96 L1202.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1202.12,1720.96 1202.12,1720.96 1202.4,1720.96 1202.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1202.4 1720.96 L1202.4 1720.96 L1202.68 1720.96 L1202.68 1720.96 L1202.4 1720.96 L1202.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1202.4,1720.96 1202.4,1720.96 1202.68,1720.96 1202.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1202.68 1720.96 L1202.68 1720.96 L1202.97 1720.96 L1202.97 1720.96 L1202.68 1720.96 L1202.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1202.68,1720.96 1202.68,1720.96 1202.97,1720.96 1202.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1202.97 1720.76 L1202.97 1720.96 L1203.25 1720.96 L1203.25 1720.76 L1202.97 1720.76 L1202.97 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1202.97,1720.76 1202.97,1720.96 1203.25,1720.96 1203.25,1720.76 1202.97,1720.76 "/>
<path clip-path="url(#clip322)" d="M1203.25 1720.96 L1203.25 1720.96 L1203.53 1720.96 L1203.53 1720.96 L1203.25 1720.96 L1203.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1203.25,1720.96 1203.25,1720.96 1203.53,1720.96 1203.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1203.53 1720.76 L1203.53 1720.96 L1203.81 1720.96 L1203.81 1720.76 L1203.53 1720.76 L1203.53 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1203.53,1720.76 1203.53,1720.96 1203.81,1720.96 1203.81,1720.76 1203.53,1720.76 "/>
<path clip-path="url(#clip322)" d="M1203.81 1720.96 L1203.81 1720.96 L1204.09 1720.96 L1204.09 1720.96 L1203.81 1720.96 L1203.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1203.81,1720.96 1203.81,1720.96 1204.09,1720.96 1203.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1204.09 1720.96 L1204.09 1720.96 L1204.37 1720.96 L1204.37 1720.96 L1204.09 1720.96 L1204.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1204.09,1720.96 1204.09,1720.96 1204.37,1720.96 1204.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1204.37 1720.96 L1204.37 1720.96 L1204.66 1720.96 L1204.66 1720.96 L1204.37 1720.96 L1204.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1204.37,1720.96 1204.37,1720.96 1204.66,1720.96 1204.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1204.66 1720.96 L1204.66 1720.96 L1204.94 1720.96 L1204.94 1720.96 L1204.66 1720.96 L1204.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1204.66,1720.96 1204.66,1720.96 1204.94,1720.96 1204.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1204.94 1720.76 L1204.94 1720.96 L1205.22 1720.96 L1205.22 1720.76 L1204.94 1720.76 L1204.94 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1204.94,1720.76 1204.94,1720.96 1205.22,1720.96 1205.22,1720.76 1204.94,1720.76 "/>
<path clip-path="url(#clip322)" d="M1205.22 1720.76 L1205.22 1720.96 L1205.5 1720.96 L1205.5 1720.76 L1205.22 1720.76 L1205.22 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1205.22,1720.76 1205.22,1720.96 1205.5,1720.96 1205.5,1720.76 1205.22,1720.76 "/>
<path clip-path="url(#clip322)" d="M1205.5 1720.76 L1205.5 1720.96 L1205.78 1720.96 L1205.78 1720.76 L1205.5 1720.76 L1205.5 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1205.5,1720.76 1205.5,1720.96 1205.78,1720.96 1205.78,1720.76 1205.5,1720.76 "/>
<path clip-path="url(#clip322)" d="M1205.78 1720.96 L1205.78 1720.96 L1206.07 1720.96 L1206.07 1720.96 L1205.78 1720.96 L1205.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1205.78,1720.96 1205.78,1720.96 1206.07,1720.96 1205.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1206.07 1720.96 L1206.07 1720.96 L1206.35 1720.96 L1206.35 1720.96 L1206.07 1720.96 L1206.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1206.07,1720.96 1206.07,1720.96 1206.35,1720.96 1206.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1206.35 1720.96 L1206.35 1720.96 L1206.63 1720.96 L1206.63 1720.96 L1206.35 1720.96 L1206.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1206.35,1720.96 1206.35,1720.96 1206.63,1720.96 1206.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1206.63 1720.96 L1206.63 1720.96 L1206.91 1720.96 L1206.91 1720.96 L1206.63 1720.96 L1206.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1206.63,1720.96 1206.63,1720.96 1206.91,1720.96 1206.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1206.91 1720.76 L1206.91 1720.96 L1207.19 1720.96 L1207.19 1720.76 L1206.91 1720.76 L1206.91 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1206.91,1720.76 1206.91,1720.96 1207.19,1720.96 1207.19,1720.76 1206.91,1720.76 "/>
<path clip-path="url(#clip322)" d="M1207.19 1720.96 L1207.19 1720.96 L1207.47 1720.96 L1207.47 1720.96 L1207.19 1720.96 L1207.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1207.19,1720.96 1207.19,1720.96 1207.47,1720.96 1207.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1207.47 1720.76 L1207.47 1720.96 L1207.76 1720.96 L1207.76 1720.76 L1207.47 1720.76 L1207.47 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1207.47,1720.76 1207.47,1720.96 1207.76,1720.96 1207.76,1720.76 1207.47,1720.76 "/>
<path clip-path="url(#clip322)" d="M1207.76 1720.96 L1207.76 1720.96 L1208.04 1720.96 L1208.04 1720.96 L1207.76 1720.96 L1207.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1207.76,1720.96 1207.76,1720.96 1208.04,1720.96 1207.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1208.04 1720.96 L1208.04 1720.96 L1208.32 1720.96 L1208.32 1720.96 L1208.04 1720.96 L1208.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1208.04,1720.96 1208.04,1720.96 1208.32,1720.96 1208.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1208.32 1720.96 L1208.32 1720.96 L1208.6 1720.96 L1208.6 1720.96 L1208.32 1720.96 L1208.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1208.32,1720.96 1208.32,1720.96 1208.6,1720.96 1208.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1208.6 1720.96 L1208.6 1720.96 L1208.88 1720.96 L1208.88 1720.96 L1208.6 1720.96 L1208.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1208.6,1720.96 1208.6,1720.96 1208.88,1720.96 1208.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1208.88 1720.96 L1208.88 1720.96 L1209.16 1720.96 L1209.16 1720.96 L1208.88 1720.96 L1208.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1208.88,1720.96 1208.88,1720.96 1209.16,1720.96 1208.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1209.16 1720.76 L1209.16 1720.96 L1209.45 1720.96 L1209.45 1720.76 L1209.16 1720.76 L1209.16 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1209.16,1720.76 1209.16,1720.96 1209.45,1720.96 1209.45,1720.76 1209.16,1720.76 "/>
<path clip-path="url(#clip322)" d="M1209.45 1720.96 L1209.45 1720.96 L1209.73 1720.96 L1209.73 1720.96 L1209.45 1720.96 L1209.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1209.45,1720.96 1209.45,1720.96 1209.73,1720.96 1209.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1209.73 1720.96 L1209.73 1720.96 L1210.01 1720.96 L1210.01 1720.96 L1209.73 1720.96 L1209.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1209.73,1720.96 1209.73,1720.96 1210.01,1720.96 1209.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1210.01 1720.96 L1210.01 1720.96 L1210.29 1720.96 L1210.29 1720.96 L1210.01 1720.96 L1210.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1210.01,1720.96 1210.01,1720.96 1210.29,1720.96 1210.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1210.29 1720.96 L1210.29 1720.96 L1210.57 1720.96 L1210.57 1720.96 L1210.29 1720.96 L1210.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1210.29,1720.96 1210.29,1720.96 1210.57,1720.96 1210.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1210.57 1720.76 L1210.57 1720.96 L1210.85 1720.96 L1210.85 1720.76 L1210.57 1720.76 L1210.57 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1210.57,1720.76 1210.57,1720.96 1210.85,1720.96 1210.85,1720.76 1210.57,1720.76 "/>
<path clip-path="url(#clip322)" d="M1210.85 1720.96 L1210.85 1720.96 L1211.14 1720.96 L1211.14 1720.96 L1210.85 1720.96 L1210.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1210.85,1720.96 1210.85,1720.96 1211.14,1720.96 1210.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1211.14 1720.96 L1211.14 1720.96 L1211.42 1720.96 L1211.42 1720.96 L1211.14 1720.96 L1211.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1211.14,1720.96 1211.14,1720.96 1211.42,1720.96 1211.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1211.42 1720.96 L1211.42 1720.96 L1211.7 1720.96 L1211.7 1720.96 L1211.42 1720.96 L1211.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1211.42,1720.96 1211.42,1720.96 1211.7,1720.96 1211.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1211.7 1720.96 L1211.7 1720.96 L1211.98 1720.96 L1211.98 1720.96 L1211.7 1720.96 L1211.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1211.7,1720.96 1211.7,1720.96 1211.98,1720.96 1211.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1211.98 1720.96 L1211.98 1720.96 L1212.26 1720.96 L1212.26 1720.96 L1211.98 1720.96 L1211.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1211.98,1720.96 1211.98,1720.96 1212.26,1720.96 1211.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1212.26 1720.96 L1212.26 1720.96 L1212.54 1720.96 L1212.54 1720.96 L1212.26 1720.96 L1212.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1212.26,1720.96 1212.26,1720.96 1212.54,1720.96 1212.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1212.54 1720.96 L1212.54 1720.96 L1212.83 1720.96 L1212.83 1720.96 L1212.54 1720.96 L1212.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1212.54,1720.96 1212.54,1720.96 1212.83,1720.96 1212.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1212.83 1720.96 L1212.83 1720.96 L1213.11 1720.96 L1213.11 1720.96 L1212.83 1720.96 L1212.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1212.83,1720.96 1212.83,1720.96 1213.11,1720.96 1212.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1213.11 1720.96 L1213.11 1720.96 L1213.39 1720.96 L1213.39 1720.96 L1213.11 1720.96 L1213.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1213.11,1720.96 1213.11,1720.96 1213.39,1720.96 1213.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1213.39 1720.96 L1213.39 1720.96 L1213.67 1720.96 L1213.67 1720.96 L1213.39 1720.96 L1213.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1213.39,1720.96 1213.39,1720.96 1213.67,1720.96 1213.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1213.67 1720.76 L1213.67 1720.96 L1213.95 1720.96 L1213.95 1720.76 L1213.67 1720.76 L1213.67 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1213.67,1720.76 1213.67,1720.96 1213.95,1720.96 1213.95,1720.76 1213.67,1720.76 "/>
<path clip-path="url(#clip322)" d="M1213.95 1720.96 L1213.95 1720.96 L1214.24 1720.96 L1214.24 1720.96 L1213.95 1720.96 L1213.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1213.95,1720.96 1213.95,1720.96 1214.24,1720.96 1213.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1214.24 1720.96 L1214.24 1720.96 L1214.52 1720.96 L1214.52 1720.96 L1214.24 1720.96 L1214.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1214.24,1720.96 1214.24,1720.96 1214.52,1720.96 1214.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1214.52 1720.96 L1214.52 1720.96 L1214.8 1720.96 L1214.8 1720.96 L1214.52 1720.96 L1214.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1214.52,1720.96 1214.52,1720.96 1214.8,1720.96 1214.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1214.8 1720.76 L1214.8 1720.96 L1215.08 1720.96 L1215.08 1720.76 L1214.8 1720.76 L1214.8 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1214.8,1720.76 1214.8,1720.96 1215.08,1720.96 1215.08,1720.76 1214.8,1720.76 "/>
<path clip-path="url(#clip322)" d="M1215.08 1720.76 L1215.08 1720.96 L1215.36 1720.96 L1215.36 1720.76 L1215.08 1720.76 L1215.08 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1215.08,1720.76 1215.08,1720.96 1215.36,1720.96 1215.36,1720.76 1215.08,1720.76 "/>
<path clip-path="url(#clip322)" d="M1215.36 1720.96 L1215.36 1720.96 L1215.64 1720.96 L1215.64 1720.96 L1215.36 1720.96 L1215.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1215.36,1720.96 1215.36,1720.96 1215.64,1720.96 1215.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1215.64 1720.96 L1215.64 1720.96 L1215.93 1720.96 L1215.93 1720.96 L1215.64 1720.96 L1215.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1215.64,1720.96 1215.64,1720.96 1215.93,1720.96 1215.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1215.93 1720.96 L1215.93 1720.96 L1216.21 1720.96 L1216.21 1720.96 L1215.93 1720.96 L1215.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1215.93,1720.96 1215.93,1720.96 1216.21,1720.96 1215.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1216.21 1720.96 L1216.21 1720.96 L1216.49 1720.96 L1216.49 1720.96 L1216.21 1720.96 L1216.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1216.21,1720.96 1216.21,1720.96 1216.49,1720.96 1216.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1216.49 1720.96 L1216.49 1720.96 L1216.77 1720.96 L1216.77 1720.96 L1216.49 1720.96 L1216.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1216.49,1720.96 1216.49,1720.96 1216.77,1720.96 1216.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1216.77 1720.96 L1216.77 1720.96 L1217.05 1720.96 L1217.05 1720.96 L1216.77 1720.96 L1216.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1216.77,1720.96 1216.77,1720.96 1217.05,1720.96 1216.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1217.05 1720.96 L1217.05 1720.96 L1217.33 1720.96 L1217.33 1720.96 L1217.05 1720.96 L1217.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1217.05,1720.96 1217.05,1720.96 1217.33,1720.96 1217.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1217.33 1720.76 L1217.33 1720.96 L1217.62 1720.96 L1217.62 1720.76 L1217.33 1720.76 L1217.33 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1217.33,1720.76 1217.33,1720.96 1217.62,1720.96 1217.62,1720.76 1217.33,1720.76 "/>
<path clip-path="url(#clip322)" d="M1217.62 1720.96 L1217.62 1720.96 L1217.9 1720.96 L1217.9 1720.96 L1217.62 1720.96 L1217.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1217.62,1720.96 1217.62,1720.96 1217.9,1720.96 1217.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1217.9 1720.96 L1217.9 1720.96 L1218.18 1720.96 L1218.18 1720.96 L1217.9 1720.96 L1217.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1217.9,1720.96 1217.9,1720.96 1218.18,1720.96 1217.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1218.18 1720.76 L1218.18 1720.96 L1218.46 1720.96 L1218.46 1720.76 L1218.18 1720.76 L1218.18 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1218.18,1720.76 1218.18,1720.96 1218.46,1720.96 1218.46,1720.76 1218.18,1720.76 "/>
<path clip-path="url(#clip322)" d="M1218.46 1720.96 L1218.46 1720.96 L1218.74 1720.96 L1218.74 1720.96 L1218.46 1720.96 L1218.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1218.46,1720.96 1218.46,1720.96 1218.74,1720.96 1218.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1218.74 1720.96 L1218.74 1720.96 L1219.02 1720.96 L1219.02 1720.96 L1218.74 1720.96 L1218.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1218.74,1720.96 1218.74,1720.96 1219.02,1720.96 1218.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1219.02 1720.96 L1219.02 1720.96 L1219.31 1720.96 L1219.31 1720.96 L1219.02 1720.96 L1219.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1219.02,1720.96 1219.02,1720.96 1219.31,1720.96 1219.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1219.31 1720.96 L1219.31 1720.96 L1219.59 1720.96 L1219.59 1720.96 L1219.31 1720.96 L1219.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1219.31,1720.96 1219.31,1720.96 1219.59,1720.96 1219.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1219.59 1720.96 L1219.59 1720.96 L1219.87 1720.96 L1219.87 1720.96 L1219.59 1720.96 L1219.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1219.59,1720.96 1219.59,1720.96 1219.87,1720.96 1219.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1219.87 1720.96 L1219.87 1720.96 L1220.15 1720.96 L1220.15 1720.96 L1219.87 1720.96 L1219.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1219.87,1720.96 1219.87,1720.96 1220.15,1720.96 1219.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1220.15 1720.96 L1220.15 1720.96 L1220.43 1720.96 L1220.43 1720.96 L1220.15 1720.96 L1220.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1220.15,1720.96 1220.15,1720.96 1220.43,1720.96 1220.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1220.43 1720.96 L1220.43 1720.96 L1220.71 1720.96 L1220.71 1720.96 L1220.43 1720.96 L1220.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1220.43,1720.96 1220.43,1720.96 1220.71,1720.96 1220.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1220.71 1720.96 L1220.71 1720.96 L1221 1720.96 L1221 1720.96 L1220.71 1720.96 L1220.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1220.71,1720.96 1220.71,1720.96 1221,1720.96 1220.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1221 1720.76 L1221 1720.96 L1221.28 1720.96 L1221.28 1720.76 L1221 1720.76 L1221 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1221,1720.76 1221,1720.96 1221.28,1720.96 1221.28,1720.76 1221,1720.76 "/>
<path clip-path="url(#clip322)" d="M1221.28 1720.96 L1221.28 1720.96 L1221.56 1720.96 L1221.56 1720.96 L1221.28 1720.96 L1221.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1221.28,1720.96 1221.28,1720.96 1221.56,1720.96 1221.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1221.56 1720.96 L1221.56 1720.96 L1221.84 1720.96 L1221.84 1720.96 L1221.56 1720.96 L1221.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1221.56,1720.96 1221.56,1720.96 1221.84,1720.96 1221.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1221.84 1720.76 L1221.84 1720.96 L1222.12 1720.96 L1222.12 1720.76 L1221.84 1720.76 L1221.84 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1221.84,1720.76 1221.84,1720.96 1222.12,1720.96 1222.12,1720.76 1221.84,1720.76 "/>
<path clip-path="url(#clip322)" d="M1222.12 1720.96 L1222.12 1720.96 L1222.41 1720.96 L1222.41 1720.96 L1222.12 1720.96 L1222.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1222.12,1720.96 1222.12,1720.96 1222.41,1720.96 1222.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1222.41 1720.96 L1222.41 1720.96 L1222.69 1720.96 L1222.69 1720.96 L1222.41 1720.96 L1222.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1222.41,1720.96 1222.41,1720.96 1222.69,1720.96 1222.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1222.69 1720.76 L1222.69 1720.96 L1222.97 1720.96 L1222.97 1720.76 L1222.69 1720.76 L1222.69 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1222.69,1720.76 1222.69,1720.96 1222.97,1720.96 1222.97,1720.76 1222.69,1720.76 "/>
<path clip-path="url(#clip322)" d="M1222.97 1720.76 L1222.97 1720.96 L1223.25 1720.96 L1223.25 1720.76 L1222.97 1720.76 L1222.97 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1222.97,1720.76 1222.97,1720.96 1223.25,1720.96 1223.25,1720.76 1222.97,1720.76 "/>
<path clip-path="url(#clip322)" d="M1223.25 1720.96 L1223.25 1720.96 L1223.53 1720.96 L1223.53 1720.96 L1223.25 1720.96 L1223.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1223.25,1720.96 1223.25,1720.96 1223.53,1720.96 1223.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1223.53 1720.96 L1223.53 1720.96 L1223.81 1720.96 L1223.81 1720.96 L1223.53 1720.96 L1223.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1223.53,1720.96 1223.53,1720.96 1223.81,1720.96 1223.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1223.81 1720.96 L1223.81 1720.96 L1224.1 1720.96 L1224.1 1720.96 L1223.81 1720.96 L1223.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1223.81,1720.96 1223.81,1720.96 1224.1,1720.96 1223.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1224.1 1720.96 L1224.1 1720.96 L1224.38 1720.96 L1224.38 1720.96 L1224.1 1720.96 L1224.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1224.1,1720.96 1224.1,1720.96 1224.38,1720.96 1224.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1224.38 1720.96 L1224.38 1720.96 L1224.66 1720.96 L1224.66 1720.96 L1224.38 1720.96 L1224.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1224.38,1720.96 1224.38,1720.96 1224.66,1720.96 1224.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1224.66 1720.96 L1224.66 1720.96 L1224.94 1720.96 L1224.94 1720.96 L1224.66 1720.96 L1224.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1224.66,1720.96 1224.66,1720.96 1224.94,1720.96 1224.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1224.94 1720.76 L1224.94 1720.96 L1225.22 1720.96 L1225.22 1720.76 L1224.94 1720.76 L1224.94 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1224.94,1720.76 1224.94,1720.96 1225.22,1720.96 1225.22,1720.76 1224.94,1720.76 "/>
<path clip-path="url(#clip322)" d="M1225.22 1720.96 L1225.22 1720.96 L1225.5 1720.96 L1225.5 1720.96 L1225.22 1720.96 L1225.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1225.22,1720.96 1225.22,1720.96 1225.5,1720.96 1225.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1225.5 1720.96 L1225.5 1720.96 L1225.79 1720.96 L1225.79 1720.96 L1225.5 1720.96 L1225.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1225.5,1720.96 1225.5,1720.96 1225.79,1720.96 1225.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1225.79 1720.96 L1225.79 1720.96 L1226.07 1720.96 L1226.07 1720.96 L1225.79 1720.96 L1225.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1225.79,1720.96 1225.79,1720.96 1226.07,1720.96 1225.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1226.07 1720.96 L1226.07 1720.96 L1226.35 1720.96 L1226.35 1720.96 L1226.07 1720.96 L1226.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1226.07,1720.96 1226.07,1720.96 1226.35,1720.96 1226.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1226.35 1720.96 L1226.35 1720.96 L1226.63 1720.96 L1226.63 1720.96 L1226.35 1720.96 L1226.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1226.35,1720.96 1226.35,1720.96 1226.63,1720.96 1226.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1226.63 1720.96 L1226.63 1720.96 L1226.91 1720.96 L1226.91 1720.96 L1226.63 1720.96 L1226.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1226.63,1720.96 1226.63,1720.96 1226.91,1720.96 1226.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1226.91 1720.96 L1226.91 1720.96 L1227.19 1720.96 L1227.19 1720.96 L1226.91 1720.96 L1226.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1226.91,1720.96 1226.91,1720.96 1227.19,1720.96 1226.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1227.19 1720.76 L1227.19 1720.96 L1227.48 1720.96 L1227.48 1720.76 L1227.19 1720.76 L1227.19 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1227.19,1720.76 1227.19,1720.96 1227.48,1720.96 1227.48,1720.76 1227.19,1720.76 "/>
<path clip-path="url(#clip322)" d="M1227.48 1720.96 L1227.48 1720.96 L1227.76 1720.96 L1227.76 1720.96 L1227.48 1720.96 L1227.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1227.48,1720.96 1227.48,1720.96 1227.76,1720.96 1227.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1227.76 1720.96 L1227.76 1720.96 L1228.04 1720.96 L1228.04 1720.96 L1227.76 1720.96 L1227.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1227.76,1720.96 1227.76,1720.96 1228.04,1720.96 1227.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1228.04 1720.96 L1228.04 1720.96 L1228.32 1720.96 L1228.32 1720.96 L1228.04 1720.96 L1228.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1228.04,1720.96 1228.04,1720.96 1228.32,1720.96 1228.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1228.32 1720.76 L1228.32 1720.96 L1228.6 1720.96 L1228.6 1720.76 L1228.32 1720.76 L1228.32 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1228.32,1720.76 1228.32,1720.96 1228.6,1720.96 1228.6,1720.76 1228.32,1720.76 "/>
<path clip-path="url(#clip322)" d="M1228.6 1720.76 L1228.6 1720.96 L1228.88 1720.96 L1228.88 1720.76 L1228.6 1720.76 L1228.6 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1228.6,1720.76 1228.6,1720.96 1228.88,1720.96 1228.88,1720.76 1228.6,1720.76 "/>
<path clip-path="url(#clip322)" d="M1228.88 1720.96 L1228.88 1720.96 L1229.17 1720.96 L1229.17 1720.96 L1228.88 1720.96 L1228.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1228.88,1720.96 1228.88,1720.96 1229.17,1720.96 1228.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1229.17 1720.96 L1229.17 1720.96 L1229.45 1720.96 L1229.45 1720.96 L1229.17 1720.96 L1229.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1229.17,1720.96 1229.17,1720.96 1229.45,1720.96 1229.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1229.45 1720.96 L1229.45 1720.96 L1229.73 1720.96 L1229.73 1720.96 L1229.45 1720.96 L1229.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1229.45,1720.96 1229.45,1720.96 1229.73,1720.96 1229.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1229.73 1720.96 L1229.73 1720.96 L1230.01 1720.96 L1230.01 1720.96 L1229.73 1720.96 L1229.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1229.73,1720.96 1229.73,1720.96 1230.01,1720.96 1229.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1230.01 1720.96 L1230.01 1720.96 L1230.29 1720.96 L1230.29 1720.96 L1230.01 1720.96 L1230.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1230.01,1720.96 1230.01,1720.96 1230.29,1720.96 1230.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1230.29 1720.96 L1230.29 1720.96 L1230.58 1720.96 L1230.58 1720.96 L1230.29 1720.96 L1230.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1230.29,1720.96 1230.29,1720.96 1230.58,1720.96 1230.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1230.58 1720.96 L1230.58 1720.96 L1230.86 1720.96 L1230.86 1720.96 L1230.58 1720.96 L1230.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1230.58,1720.96 1230.58,1720.96 1230.86,1720.96 1230.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1230.86 1720.96 L1230.86 1720.96 L1231.14 1720.96 L1231.14 1720.96 L1230.86 1720.96 L1230.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1230.86,1720.96 1230.86,1720.96 1231.14,1720.96 1230.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1231.14 1720.96 L1231.14 1720.96 L1231.42 1720.96 L1231.42 1720.96 L1231.14 1720.96 L1231.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1231.14,1720.96 1231.14,1720.96 1231.42,1720.96 1231.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1231.42 1720.96 L1231.42 1720.96 L1231.7 1720.96 L1231.7 1720.96 L1231.42 1720.96 L1231.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1231.42,1720.96 1231.42,1720.96 1231.7,1720.96 1231.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1231.7 1720.96 L1231.7 1720.96 L1231.98 1720.96 L1231.98 1720.96 L1231.7 1720.96 L1231.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1231.7,1720.96 1231.7,1720.96 1231.98,1720.96 1231.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1231.98 1720.96 L1231.98 1720.96 L1232.27 1720.96 L1232.27 1720.96 L1231.98 1720.96 L1231.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1231.98,1720.96 1231.98,1720.96 1232.27,1720.96 1231.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1232.27 1720.96 L1232.27 1720.96 L1232.55 1720.96 L1232.55 1720.96 L1232.27 1720.96 L1232.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1232.27,1720.96 1232.27,1720.96 1232.55,1720.96 1232.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1232.55 1720.96 L1232.55 1720.96 L1232.83 1720.96 L1232.83 1720.96 L1232.55 1720.96 L1232.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1232.55,1720.96 1232.55,1720.96 1232.83,1720.96 1232.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1232.83 1720.76 L1232.83 1720.96 L1233.11 1720.96 L1233.11 1720.76 L1232.83 1720.76 L1232.83 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1232.83,1720.76 1232.83,1720.96 1233.11,1720.96 1233.11,1720.76 1232.83,1720.76 "/>
<path clip-path="url(#clip322)" d="M1233.11 1720.96 L1233.11 1720.96 L1233.39 1720.96 L1233.39 1720.96 L1233.11 1720.96 L1233.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1233.11,1720.96 1233.11,1720.96 1233.39,1720.96 1233.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1233.39 1720.96 L1233.39 1720.96 L1233.67 1720.96 L1233.67 1720.96 L1233.39 1720.96 L1233.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1233.39,1720.96 1233.39,1720.96 1233.67,1720.96 1233.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1233.67 1720.76 L1233.67 1720.96 L1233.96 1720.96 L1233.96 1720.76 L1233.67 1720.76 L1233.67 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1233.67,1720.76 1233.67,1720.96 1233.96,1720.96 1233.96,1720.76 1233.67,1720.76 "/>
<path clip-path="url(#clip322)" d="M1233.96 1720.96 L1233.96 1720.96 L1234.24 1720.96 L1234.24 1720.96 L1233.96 1720.96 L1233.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1233.96,1720.96 1233.96,1720.96 1234.24,1720.96 1233.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1234.24 1720.96 L1234.24 1720.96 L1234.52 1720.96 L1234.52 1720.96 L1234.24 1720.96 L1234.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1234.24,1720.96 1234.24,1720.96 1234.52,1720.96 1234.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1234.52 1720.96 L1234.52 1720.96 L1234.8 1720.96 L1234.8 1720.96 L1234.52 1720.96 L1234.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1234.52,1720.96 1234.52,1720.96 1234.8,1720.96 1234.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1234.8 1720.76 L1234.8 1720.96 L1235.08 1720.96 L1235.08 1720.76 L1234.8 1720.76 L1234.8 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1234.8,1720.76 1234.8,1720.96 1235.08,1720.96 1235.08,1720.76 1234.8,1720.76 "/>
<path clip-path="url(#clip322)" d="M1235.08 1720.76 L1235.08 1720.96 L1235.36 1720.96 L1235.36 1720.76 L1235.08 1720.76 L1235.08 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1235.08,1720.76 1235.08,1720.96 1235.36,1720.96 1235.36,1720.76 1235.08,1720.76 "/>
<path clip-path="url(#clip322)" d="M1235.36 1720.96 L1235.36 1720.96 L1235.65 1720.96 L1235.65 1720.96 L1235.36 1720.96 L1235.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1235.36,1720.96 1235.36,1720.96 1235.65,1720.96 1235.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1235.65 1720.96 L1235.65 1720.96 L1235.93 1720.96 L1235.93 1720.96 L1235.65 1720.96 L1235.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1235.65,1720.96 1235.65,1720.96 1235.93,1720.96 1235.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1235.93 1720.96 L1235.93 1720.96 L1236.21 1720.96 L1236.21 1720.96 L1235.93 1720.96 L1235.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1235.93,1720.96 1235.93,1720.96 1236.21,1720.96 1235.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1236.21 1720.76 L1236.21 1720.96 L1236.49 1720.96 L1236.49 1720.76 L1236.21 1720.76 L1236.21 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1236.21,1720.76 1236.21,1720.96 1236.49,1720.96 1236.49,1720.76 1236.21,1720.76 "/>
<path clip-path="url(#clip322)" d="M1236.49 1720.96 L1236.49 1720.96 L1236.77 1720.96 L1236.77 1720.96 L1236.49 1720.96 L1236.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1236.49,1720.96 1236.49,1720.96 1236.77,1720.96 1236.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1236.77 1720.96 L1236.77 1720.96 L1237.05 1720.96 L1237.05 1720.96 L1236.77 1720.96 L1236.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1236.77,1720.96 1236.77,1720.96 1237.05,1720.96 1236.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1237.05 1720.96 L1237.05 1720.96 L1237.34 1720.96 L1237.34 1720.96 L1237.05 1720.96 L1237.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1237.05,1720.96 1237.05,1720.96 1237.34,1720.96 1237.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1237.34 1720.76 L1237.34 1720.96 L1237.62 1720.96 L1237.62 1720.76 L1237.34 1720.76 L1237.34 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1237.34,1720.76 1237.34,1720.96 1237.62,1720.96 1237.62,1720.76 1237.34,1720.76 "/>
<path clip-path="url(#clip322)" d="M1237.62 1720.96 L1237.62 1720.96 L1237.9 1720.96 L1237.9 1720.96 L1237.62 1720.96 L1237.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1237.62,1720.96 1237.62,1720.96 1237.9,1720.96 1237.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1237.9 1720.96 L1237.9 1720.96 L1238.18 1720.96 L1238.18 1720.96 L1237.9 1720.96 L1237.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1237.9,1720.96 1237.9,1720.96 1238.18,1720.96 1237.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1238.18 1720.96 L1238.18 1720.96 L1238.46 1720.96 L1238.46 1720.96 L1238.18 1720.96 L1238.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1238.18,1720.96 1238.18,1720.96 1238.46,1720.96 1238.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1238.46 1720.96 L1238.46 1720.96 L1238.75 1720.96 L1238.75 1720.96 L1238.46 1720.96 L1238.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1238.46,1720.96 1238.46,1720.96 1238.75,1720.96 1238.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1238.75 1720.96 L1238.75 1720.96 L1239.03 1720.96 L1239.03 1720.96 L1238.75 1720.96 L1238.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1238.75,1720.96 1238.75,1720.96 1239.03,1720.96 1238.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1239.03 1720.96 L1239.03 1720.96 L1239.31 1720.96 L1239.31 1720.96 L1239.03 1720.96 L1239.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1239.03,1720.96 1239.03,1720.96 1239.31,1720.96 1239.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1239.31 1720.96 L1239.31 1720.96 L1239.59 1720.96 L1239.59 1720.96 L1239.31 1720.96 L1239.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1239.31,1720.96 1239.31,1720.96 1239.59,1720.96 1239.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1239.59 1720.76 L1239.59 1720.96 L1239.87 1720.96 L1239.87 1720.76 L1239.59 1720.76 L1239.59 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1239.59,1720.76 1239.59,1720.96 1239.87,1720.96 1239.87,1720.76 1239.59,1720.76 "/>
<path clip-path="url(#clip322)" d="M1239.87 1720.96 L1239.87 1720.96 L1240.15 1720.96 L1240.15 1720.96 L1239.87 1720.96 L1239.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1239.87,1720.96 1239.87,1720.96 1240.15,1720.96 1239.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1240.15 1720.96 L1240.15 1720.96 L1240.44 1720.96 L1240.44 1720.96 L1240.15 1720.96 L1240.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1240.15,1720.96 1240.15,1720.96 1240.44,1720.96 1240.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1240.44 1720.96 L1240.44 1720.96 L1240.72 1720.96 L1240.72 1720.96 L1240.44 1720.96 L1240.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1240.44,1720.96 1240.44,1720.96 1240.72,1720.96 1240.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1240.72 1720.96 L1240.72 1720.96 L1241 1720.96 L1241 1720.96 L1240.72 1720.96 L1240.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1240.72,1720.96 1240.72,1720.96 1241,1720.96 1240.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1241 1720.96 L1241 1720.96 L1241.28 1720.96 L1241.28 1720.96 L1241 1720.96 L1241 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1241,1720.96 1241,1720.96 1241.28,1720.96 1241,1720.96 "/>
<path clip-path="url(#clip322)" d="M1241.28 1720.96 L1241.28 1720.96 L1241.56 1720.96 L1241.56 1720.96 L1241.28 1720.96 L1241.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1241.28,1720.96 1241.28,1720.96 1241.56,1720.96 1241.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1241.56 1720.96 L1241.56 1720.96 L1241.84 1720.96 L1241.84 1720.96 L1241.56 1720.96 L1241.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1241.56,1720.96 1241.56,1720.96 1241.84,1720.96 1241.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1241.84 1720.96 L1241.84 1720.96 L1242.13 1720.96 L1242.13 1720.96 L1241.84 1720.96 L1241.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1241.84,1720.96 1241.84,1720.96 1242.13,1720.96 1241.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1242.13 1720.96 L1242.13 1720.96 L1242.41 1720.96 L1242.41 1720.96 L1242.13 1720.96 L1242.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1242.13,1720.96 1242.13,1720.96 1242.41,1720.96 1242.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1242.41 1720.96 L1242.41 1720.96 L1242.69 1720.96 L1242.69 1720.96 L1242.41 1720.96 L1242.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1242.41,1720.96 1242.41,1720.96 1242.69,1720.96 1242.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1242.69 1720.96 L1242.69 1720.96 L1242.97 1720.96 L1242.97 1720.96 L1242.69 1720.96 L1242.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1242.69,1720.96 1242.69,1720.96 1242.97,1720.96 1242.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1242.97 1720.76 L1242.97 1720.96 L1243.25 1720.96 L1243.25 1720.76 L1242.97 1720.76 L1242.97 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1242.97,1720.76 1242.97,1720.96 1243.25,1720.96 1243.25,1720.76 1242.97,1720.76 "/>
<path clip-path="url(#clip322)" d="M1243.25 1720.96 L1243.25 1720.96 L1243.53 1720.96 L1243.53 1720.96 L1243.25 1720.96 L1243.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1243.25,1720.96 1243.25,1720.96 1243.53,1720.96 1243.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1243.53 1720.96 L1243.53 1720.96 L1243.82 1720.96 L1243.82 1720.96 L1243.53 1720.96 L1243.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1243.53,1720.96 1243.53,1720.96 1243.82,1720.96 1243.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1243.82 1720.96 L1243.82 1720.96 L1244.1 1720.96 L1244.1 1720.96 L1243.82 1720.96 L1243.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1243.82,1720.96 1243.82,1720.96 1244.1,1720.96 1243.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1244.1 1720.96 L1244.1 1720.96 L1244.38 1720.96 L1244.38 1720.96 L1244.1 1720.96 L1244.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1244.1,1720.96 1244.1,1720.96 1244.38,1720.96 1244.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1244.38 1720.96 L1244.38 1720.96 L1244.66 1720.96 L1244.66 1720.96 L1244.38 1720.96 L1244.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1244.38,1720.96 1244.38,1720.96 1244.66,1720.96 1244.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1244.66 1720.96 L1244.66 1720.96 L1244.94 1720.96 L1244.94 1720.96 L1244.66 1720.96 L1244.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1244.66,1720.96 1244.66,1720.96 1244.94,1720.96 1244.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1244.94 1720.96 L1244.94 1720.96 L1245.22 1720.96 L1245.22 1720.96 L1244.94 1720.96 L1244.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1244.94,1720.96 1244.94,1720.96 1245.22,1720.96 1244.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1245.22 1720.96 L1245.22 1720.96 L1245.51 1720.96 L1245.51 1720.96 L1245.22 1720.96 L1245.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1245.22,1720.96 1245.22,1720.96 1245.51,1720.96 1245.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1245.51 1720.96 L1245.51 1720.96 L1245.79 1720.96 L1245.79 1720.96 L1245.51 1720.96 L1245.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1245.51,1720.96 1245.51,1720.96 1245.79,1720.96 1245.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1245.79 1720.96 L1245.79 1720.96 L1246.07 1720.96 L1246.07 1720.96 L1245.79 1720.96 L1245.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1245.79,1720.96 1245.79,1720.96 1246.07,1720.96 1245.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1246.07 1720.76 L1246.07 1720.96 L1246.35 1720.96 L1246.35 1720.76 L1246.07 1720.76 L1246.07 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1246.07,1720.76 1246.07,1720.96 1246.35,1720.96 1246.35,1720.76 1246.07,1720.76 "/>
<path clip-path="url(#clip322)" d="M1246.35 1720.96 L1246.35 1720.96 L1246.63 1720.96 L1246.63 1720.96 L1246.35 1720.96 L1246.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1246.35,1720.96 1246.35,1720.96 1246.63,1720.96 1246.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1246.63 1720.96 L1246.63 1720.96 L1246.92 1720.96 L1246.92 1720.96 L1246.63 1720.96 L1246.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1246.63,1720.96 1246.63,1720.96 1246.92,1720.96 1246.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1246.92 1720.96 L1246.92 1720.96 L1247.2 1720.96 L1247.2 1720.96 L1246.92 1720.96 L1246.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1246.92,1720.96 1246.92,1720.96 1247.2,1720.96 1246.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1247.2 1720.96 L1247.2 1720.96 L1247.48 1720.96 L1247.48 1720.96 L1247.2 1720.96 L1247.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1247.2,1720.96 1247.2,1720.96 1247.48,1720.96 1247.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1247.48 1720.96 L1247.48 1720.96 L1247.76 1720.96 L1247.76 1720.96 L1247.48 1720.96 L1247.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1247.48,1720.96 1247.48,1720.96 1247.76,1720.96 1247.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1247.76 1720.96 L1247.76 1720.96 L1248.04 1720.96 L1248.04 1720.96 L1247.76 1720.96 L1247.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1247.76,1720.96 1247.76,1720.96 1248.04,1720.96 1247.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1248.04 1720.96 L1248.04 1720.96 L1248.32 1720.96 L1248.32 1720.96 L1248.04 1720.96 L1248.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1248.04,1720.96 1248.04,1720.96 1248.32,1720.96 1248.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1248.32 1720.76 L1248.32 1720.96 L1248.61 1720.96 L1248.61 1720.76 L1248.32 1720.76 L1248.32 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1248.32,1720.76 1248.32,1720.96 1248.61,1720.96 1248.61,1720.76 1248.32,1720.76 "/>
<path clip-path="url(#clip322)" d="M1248.61 1720.96 L1248.61 1720.96 L1248.89 1720.96 L1248.89 1720.96 L1248.61 1720.96 L1248.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1248.61,1720.96 1248.61,1720.96 1248.89,1720.96 1248.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1248.89 1720.96 L1248.89 1720.96 L1249.17 1720.96 L1249.17 1720.96 L1248.89 1720.96 L1248.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1248.89,1720.96 1248.89,1720.96 1249.17,1720.96 1248.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1249.17 1720.96 L1249.17 1720.96 L1249.45 1720.96 L1249.45 1720.96 L1249.17 1720.96 L1249.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1249.17,1720.96 1249.17,1720.96 1249.45,1720.96 1249.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1249.45 1720.96 L1249.45 1720.96 L1249.73 1720.96 L1249.73 1720.96 L1249.45 1720.96 L1249.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1249.45,1720.96 1249.45,1720.96 1249.73,1720.96 1249.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1249.73 1720.96 L1249.73 1720.96 L1250.01 1720.96 L1250.01 1720.96 L1249.73 1720.96 L1249.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1249.73,1720.96 1249.73,1720.96 1250.01,1720.96 1249.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1250.01 1720.96 L1250.01 1720.96 L1250.3 1720.96 L1250.3 1720.96 L1250.01 1720.96 L1250.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1250.01,1720.96 1250.01,1720.96 1250.3,1720.96 1250.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1250.3 1720.76 L1250.3 1720.96 L1250.58 1720.96 L1250.58 1720.76 L1250.3 1720.76 L1250.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1250.3,1720.76 1250.3,1720.96 1250.58,1720.96 1250.58,1720.76 1250.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1250.58 1720.96 L1250.58 1720.96 L1250.86 1720.96 L1250.86 1720.96 L1250.58 1720.96 L1250.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1250.58,1720.96 1250.58,1720.96 1250.86,1720.96 1250.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1250.86 1720.76 L1250.86 1720.96 L1251.14 1720.96 L1251.14 1720.76 L1250.86 1720.76 L1250.86 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1250.86,1720.76 1250.86,1720.96 1251.14,1720.96 1251.14,1720.76 1250.86,1720.76 "/>
<path clip-path="url(#clip322)" d="M1251.14 1720.96 L1251.14 1720.96 L1251.42 1720.96 L1251.42 1720.96 L1251.14 1720.96 L1251.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1251.14,1720.96 1251.14,1720.96 1251.42,1720.96 1251.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1251.42 1720.96 L1251.42 1720.96 L1251.7 1720.96 L1251.7 1720.96 L1251.42 1720.96 L1251.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1251.42,1720.96 1251.42,1720.96 1251.7,1720.96 1251.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1251.7 1720.96 L1251.7 1720.96 L1251.99 1720.96 L1251.99 1720.96 L1251.7 1720.96 L1251.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1251.7,1720.96 1251.7,1720.96 1251.99,1720.96 1251.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1251.99 1720.76 L1251.99 1720.96 L1252.27 1720.96 L1252.27 1720.76 L1251.99 1720.76 L1251.99 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1251.99,1720.76 1251.99,1720.96 1252.27,1720.96 1252.27,1720.76 1251.99,1720.76 "/>
<path clip-path="url(#clip322)" d="M1252.27 1720.96 L1252.27 1720.96 L1252.55 1720.96 L1252.55 1720.96 L1252.27 1720.96 L1252.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1252.27,1720.96 1252.27,1720.96 1252.55,1720.96 1252.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1252.55 1720.96 L1252.55 1720.96 L1252.83 1720.96 L1252.83 1720.96 L1252.55 1720.96 L1252.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1252.55,1720.96 1252.55,1720.96 1252.83,1720.96 1252.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1252.83 1720.96 L1252.83 1720.96 L1253.11 1720.96 L1253.11 1720.96 L1252.83 1720.96 L1252.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1252.83,1720.96 1252.83,1720.96 1253.11,1720.96 1252.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1253.11 1720.96 L1253.11 1720.96 L1253.4 1720.96 L1253.4 1720.96 L1253.11 1720.96 L1253.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1253.11,1720.96 1253.11,1720.96 1253.4,1720.96 1253.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1253.4 1720.96 L1253.4 1720.96 L1253.68 1720.96 L1253.68 1720.96 L1253.4 1720.96 L1253.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1253.4,1720.96 1253.4,1720.96 1253.68,1720.96 1253.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1253.68 1720.96 L1253.68 1720.96 L1253.96 1720.96 L1253.96 1720.96 L1253.68 1720.96 L1253.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1253.68,1720.96 1253.68,1720.96 1253.96,1720.96 1253.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1253.96 1720.96 L1253.96 1720.96 L1254.24 1720.96 L1254.24 1720.96 L1253.96 1720.96 L1253.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1253.96,1720.96 1253.96,1720.96 1254.24,1720.96 1253.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1254.24 1720.96 L1254.24 1720.96 L1254.52 1720.96 L1254.52 1720.96 L1254.24 1720.96 L1254.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1254.24,1720.96 1254.24,1720.96 1254.52,1720.96 1254.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1254.52 1720.96 L1254.52 1720.96 L1254.8 1720.96 L1254.8 1720.96 L1254.52 1720.96 L1254.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1254.52,1720.96 1254.52,1720.96 1254.8,1720.96 1254.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1254.8 1720.76 L1254.8 1720.96 L1255.09 1720.96 L1255.09 1720.76 L1254.8 1720.76 L1254.8 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1254.8,1720.76 1254.8,1720.96 1255.09,1720.96 1255.09,1720.76 1254.8,1720.76 "/>
<path clip-path="url(#clip322)" d="M1255.09 1720.37 L1255.09 1720.96 L1255.37 1720.96 L1255.37 1720.37 L1255.09 1720.37 L1255.09 1720.37  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1255.09,1720.37 1255.09,1720.96 1255.37,1720.96 1255.37,1720.37 1255.09,1720.37 "/>
<path clip-path="url(#clip322)" d="M1255.37 1720.56 L1255.37 1720.96 L1255.65 1720.96 L1255.65 1720.56 L1255.37 1720.56 L1255.37 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1255.37,1720.56 1255.37,1720.96 1255.65,1720.96 1255.65,1720.56 1255.37,1720.56 "/>
<path clip-path="url(#clip322)" d="M1255.65 1720.96 L1255.65 1720.96 L1255.93 1720.96 L1255.93 1720.96 L1255.65 1720.96 L1255.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1255.65,1720.96 1255.65,1720.96 1255.93,1720.96 1255.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1255.93 1720.76 L1255.93 1720.96 L1256.21 1720.96 L1256.21 1720.76 L1255.93 1720.76 L1255.93 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1255.93,1720.76 1255.93,1720.96 1256.21,1720.96 1256.21,1720.76 1255.93,1720.76 "/>
<path clip-path="url(#clip322)" d="M1256.21 1720.96 L1256.21 1720.96 L1256.49 1720.96 L1256.49 1720.96 L1256.21 1720.96 L1256.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1256.21,1720.96 1256.21,1720.96 1256.49,1720.96 1256.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1256.49 1720.96 L1256.49 1720.96 L1256.78 1720.96 L1256.78 1720.96 L1256.49 1720.96 L1256.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1256.49,1720.96 1256.49,1720.96 1256.78,1720.96 1256.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1256.78 1720.96 L1256.78 1720.96 L1257.06 1720.96 L1257.06 1720.96 L1256.78 1720.96 L1256.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1256.78,1720.96 1256.78,1720.96 1257.06,1720.96 1256.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1257.06 1720.96 L1257.06 1720.96 L1257.34 1720.96 L1257.34 1720.96 L1257.06 1720.96 L1257.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1257.06,1720.96 1257.06,1720.96 1257.34,1720.96 1257.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1257.34 1720.96 L1257.34 1720.96 L1257.62 1720.96 L1257.62 1720.96 L1257.34 1720.96 L1257.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1257.34,1720.96 1257.34,1720.96 1257.62,1720.96 1257.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1257.62 1720.96 L1257.62 1720.96 L1257.9 1720.96 L1257.9 1720.96 L1257.62 1720.96 L1257.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1257.62,1720.96 1257.62,1720.96 1257.9,1720.96 1257.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1257.9 1720.76 L1257.9 1720.96 L1258.18 1720.96 L1258.18 1720.76 L1257.9 1720.76 L1257.9 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1257.9,1720.76 1257.9,1720.96 1258.18,1720.96 1258.18,1720.76 1257.9,1720.76 "/>
<path clip-path="url(#clip322)" d="M1258.18 1720.96 L1258.18 1720.96 L1258.47 1720.96 L1258.47 1720.96 L1258.18 1720.96 L1258.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1258.18,1720.96 1258.18,1720.96 1258.47,1720.96 1258.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1258.47 1720.76 L1258.47 1720.96 L1258.75 1720.96 L1258.75 1720.76 L1258.47 1720.76 L1258.47 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1258.47,1720.76 1258.47,1720.96 1258.75,1720.96 1258.75,1720.76 1258.47,1720.76 "/>
<path clip-path="url(#clip322)" d="M1258.75 1720.76 L1258.75 1720.96 L1259.03 1720.96 L1259.03 1720.76 L1258.75 1720.76 L1258.75 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1258.75,1720.76 1258.75,1720.96 1259.03,1720.96 1259.03,1720.76 1258.75,1720.76 "/>
<path clip-path="url(#clip322)" d="M1259.03 1720.96 L1259.03 1720.96 L1259.31 1720.96 L1259.31 1720.96 L1259.03 1720.96 L1259.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1259.03,1720.96 1259.03,1720.96 1259.31,1720.96 1259.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1259.31 1720.96 L1259.31 1720.96 L1259.59 1720.96 L1259.59 1720.96 L1259.31 1720.96 L1259.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1259.31,1720.96 1259.31,1720.96 1259.59,1720.96 1259.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1259.59 1720.96 L1259.59 1720.96 L1259.87 1720.96 L1259.87 1720.96 L1259.59 1720.96 L1259.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1259.59,1720.96 1259.59,1720.96 1259.87,1720.96 1259.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1259.87 1720.96 L1259.87 1720.96 L1260.16 1720.96 L1260.16 1720.96 L1259.87 1720.96 L1259.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1259.87,1720.96 1259.87,1720.96 1260.16,1720.96 1259.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1260.16 1720.96 L1260.16 1720.96 L1260.44 1720.96 L1260.44 1720.96 L1260.16 1720.96 L1260.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1260.16,1720.96 1260.16,1720.96 1260.44,1720.96 1260.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1260.44 1720.96 L1260.44 1720.96 L1260.72 1720.96 L1260.72 1720.96 L1260.44 1720.96 L1260.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1260.44,1720.96 1260.44,1720.96 1260.72,1720.96 1260.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1260.72 1720.96 L1260.72 1720.96 L1261 1720.96 L1261 1720.96 L1260.72 1720.96 L1260.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1260.72,1720.96 1260.72,1720.96 1261,1720.96 1260.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1261 1720.96 L1261 1720.96 L1261.28 1720.96 L1261.28 1720.96 L1261 1720.96 L1261 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1261,1720.96 1261,1720.96 1261.28,1720.96 1261,1720.96 "/>
<path clip-path="url(#clip322)" d="M1261.28 1720.96 L1261.28 1720.96 L1261.57 1720.96 L1261.57 1720.96 L1261.28 1720.96 L1261.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1261.28,1720.96 1261.28,1720.96 1261.57,1720.96 1261.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1261.57 1720.96 L1261.57 1720.96 L1261.85 1720.96 L1261.85 1720.96 L1261.57 1720.96 L1261.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1261.57,1720.96 1261.57,1720.96 1261.85,1720.96 1261.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1261.85 1720.76 L1261.85 1720.96 L1262.13 1720.96 L1262.13 1720.76 L1261.85 1720.76 L1261.85 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1261.85,1720.76 1261.85,1720.96 1262.13,1720.96 1262.13,1720.76 1261.85,1720.76 "/>
<path clip-path="url(#clip322)" d="M1262.13 1720.96 L1262.13 1720.96 L1262.41 1720.96 L1262.41 1720.96 L1262.13 1720.96 L1262.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1262.13,1720.96 1262.13,1720.96 1262.41,1720.96 1262.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1262.41 1720.96 L1262.41 1720.96 L1262.69 1720.96 L1262.69 1720.96 L1262.41 1720.96 L1262.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1262.41,1720.96 1262.41,1720.96 1262.69,1720.96 1262.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1262.69 1720.96 L1262.69 1720.96 L1262.97 1720.96 L1262.97 1720.96 L1262.69 1720.96 L1262.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1262.69,1720.96 1262.69,1720.96 1262.97,1720.96 1262.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1262.97 1720.76 L1262.97 1720.96 L1263.26 1720.96 L1263.26 1720.76 L1262.97 1720.76 L1262.97 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1262.97,1720.76 1262.97,1720.96 1263.26,1720.96 1263.26,1720.76 1262.97,1720.76 "/>
<path clip-path="url(#clip322)" d="M1263.26 1720.96 L1263.26 1720.96 L1263.54 1720.96 L1263.54 1720.96 L1263.26 1720.96 L1263.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1263.26,1720.96 1263.26,1720.96 1263.54,1720.96 1263.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1263.54 1720.96 L1263.54 1720.96 L1263.82 1720.96 L1263.82 1720.96 L1263.54 1720.96 L1263.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1263.54,1720.96 1263.54,1720.96 1263.82,1720.96 1263.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1263.82 1720.96 L1263.82 1720.96 L1264.1 1720.96 L1264.1 1720.96 L1263.82 1720.96 L1263.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1263.82,1720.96 1263.82,1720.96 1264.1,1720.96 1263.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1264.1 1720.96 L1264.1 1720.96 L1264.38 1720.96 L1264.38 1720.96 L1264.1 1720.96 L1264.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1264.1,1720.96 1264.1,1720.96 1264.38,1720.96 1264.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1264.38 1720.96 L1264.38 1720.96 L1264.66 1720.96 L1264.66 1720.96 L1264.38 1720.96 L1264.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1264.38,1720.96 1264.38,1720.96 1264.66,1720.96 1264.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1264.66 1720.96 L1264.66 1720.96 L1264.95 1720.96 L1264.95 1720.96 L1264.66 1720.96 L1264.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1264.66,1720.96 1264.66,1720.96 1264.95,1720.96 1264.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1264.95 1720.96 L1264.95 1720.96 L1265.23 1720.96 L1265.23 1720.96 L1264.95 1720.96 L1264.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1264.95,1720.96 1264.95,1720.96 1265.23,1720.96 1264.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1265.23 1720.96 L1265.23 1720.96 L1265.51 1720.96 L1265.51 1720.96 L1265.23 1720.96 L1265.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1265.23,1720.96 1265.23,1720.96 1265.51,1720.96 1265.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1265.51 1720.96 L1265.51 1720.96 L1265.79 1720.96 L1265.79 1720.96 L1265.51 1720.96 L1265.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1265.51,1720.96 1265.51,1720.96 1265.79,1720.96 1265.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1265.79 1720.96 L1265.79 1720.96 L1266.07 1720.96 L1266.07 1720.96 L1265.79 1720.96 L1265.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1265.79,1720.96 1265.79,1720.96 1266.07,1720.96 1265.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1266.07 1720.76 L1266.07 1720.96 L1266.35 1720.96 L1266.35 1720.76 L1266.07 1720.76 L1266.07 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1266.07,1720.76 1266.07,1720.96 1266.35,1720.96 1266.35,1720.76 1266.07,1720.76 "/>
<path clip-path="url(#clip322)" d="M1266.35 1720.96 L1266.35 1720.96 L1266.64 1720.96 L1266.64 1720.96 L1266.35 1720.96 L1266.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1266.35,1720.96 1266.35,1720.96 1266.64,1720.96 1266.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1266.64 1720.96 L1266.64 1720.96 L1266.92 1720.96 L1266.92 1720.96 L1266.64 1720.96 L1266.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1266.64,1720.96 1266.64,1720.96 1266.92,1720.96 1266.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1266.92 1720.96 L1266.92 1720.96 L1267.2 1720.96 L1267.2 1720.96 L1266.92 1720.96 L1266.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1266.92,1720.96 1266.92,1720.96 1267.2,1720.96 1266.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1267.2 1720.96 L1267.2 1720.96 L1267.48 1720.96 L1267.48 1720.96 L1267.2 1720.96 L1267.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1267.2,1720.96 1267.2,1720.96 1267.48,1720.96 1267.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1267.48 1720.76 L1267.48 1720.96 L1267.76 1720.96 L1267.76 1720.76 L1267.48 1720.76 L1267.48 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1267.48,1720.76 1267.48,1720.96 1267.76,1720.96 1267.76,1720.76 1267.48,1720.76 "/>
<path clip-path="url(#clip322)" d="M1267.76 1720.96 L1267.76 1720.96 L1268.04 1720.96 L1268.04 1720.96 L1267.76 1720.96 L1267.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1267.76,1720.96 1267.76,1720.96 1268.04,1720.96 1267.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1268.04 1720.96 L1268.04 1720.96 L1268.33 1720.96 L1268.33 1720.96 L1268.04 1720.96 L1268.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1268.04,1720.96 1268.04,1720.96 1268.33,1720.96 1268.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1268.33 1720.96 L1268.33 1720.96 L1268.61 1720.96 L1268.61 1720.96 L1268.33 1720.96 L1268.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1268.33,1720.96 1268.33,1720.96 1268.61,1720.96 1268.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1268.61 1720.96 L1268.61 1720.96 L1268.89 1720.96 L1268.89 1720.96 L1268.61 1720.96 L1268.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1268.61,1720.96 1268.61,1720.96 1268.89,1720.96 1268.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1268.89 1720.96 L1268.89 1720.96 L1269.17 1720.96 L1269.17 1720.96 L1268.89 1720.96 L1268.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1268.89,1720.96 1268.89,1720.96 1269.17,1720.96 1268.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1269.17 1720.96 L1269.17 1720.96 L1269.45 1720.96 L1269.45 1720.96 L1269.17 1720.96 L1269.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1269.17,1720.96 1269.17,1720.96 1269.45,1720.96 1269.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1269.45 1720.76 L1269.45 1720.96 L1269.74 1720.96 L1269.74 1720.76 L1269.45 1720.76 L1269.45 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1269.45,1720.76 1269.45,1720.96 1269.74,1720.96 1269.74,1720.76 1269.45,1720.76 "/>
<path clip-path="url(#clip322)" d="M1269.74 1720.96 L1269.74 1720.96 L1270.02 1720.96 L1270.02 1720.96 L1269.74 1720.96 L1269.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1269.74,1720.96 1269.74,1720.96 1270.02,1720.96 1269.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1270.02 1720.96 L1270.02 1720.96 L1270.3 1720.96 L1270.3 1720.96 L1270.02 1720.96 L1270.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1270.02,1720.96 1270.02,1720.96 1270.3,1720.96 1270.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1270.3 1720.96 L1270.3 1720.96 L1270.58 1720.96 L1270.58 1720.96 L1270.3 1720.96 L1270.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1270.3,1720.96 1270.3,1720.96 1270.58,1720.96 1270.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1270.58 1720.76 L1270.58 1720.96 L1270.86 1720.96 L1270.86 1720.76 L1270.58 1720.76 L1270.58 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1270.58,1720.76 1270.58,1720.96 1270.86,1720.96 1270.86,1720.76 1270.58,1720.76 "/>
<path clip-path="url(#clip322)" d="M1270.86 1720.96 L1270.86 1720.96 L1271.14 1720.96 L1271.14 1720.96 L1270.86 1720.96 L1270.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1270.86,1720.96 1270.86,1720.96 1271.14,1720.96 1270.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1271.14 1720.96 L1271.14 1720.96 L1271.43 1720.96 L1271.43 1720.96 L1271.14 1720.96 L1271.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1271.14,1720.96 1271.14,1720.96 1271.43,1720.96 1271.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1271.43 1720.96 L1271.43 1720.96 L1271.71 1720.96 L1271.71 1720.96 L1271.43 1720.96 L1271.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1271.43,1720.96 1271.43,1720.96 1271.71,1720.96 1271.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1271.71 1720.76 L1271.71 1720.96 L1271.99 1720.96 L1271.99 1720.76 L1271.71 1720.76 L1271.71 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1271.71,1720.76 1271.71,1720.96 1271.99,1720.96 1271.99,1720.76 1271.71,1720.76 "/>
<path clip-path="url(#clip322)" d="M1271.99 1720.96 L1271.99 1720.96 L1272.27 1720.96 L1272.27 1720.96 L1271.99 1720.96 L1271.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1271.99,1720.96 1271.99,1720.96 1272.27,1720.96 1271.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1272.27 1720.96 L1272.27 1720.96 L1272.55 1720.96 L1272.55 1720.96 L1272.27 1720.96 L1272.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1272.27,1720.96 1272.27,1720.96 1272.55,1720.96 1272.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1272.55 1720.96 L1272.55 1720.96 L1272.83 1720.96 L1272.83 1720.96 L1272.55 1720.96 L1272.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1272.55,1720.96 1272.55,1720.96 1272.83,1720.96 1272.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1272.83 1720.96 L1272.83 1720.96 L1273.12 1720.96 L1273.12 1720.96 L1272.83 1720.96 L1272.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1272.83,1720.96 1272.83,1720.96 1273.12,1720.96 1272.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1273.12 1720.96 L1273.12 1720.96 L1273.4 1720.96 L1273.4 1720.96 L1273.12 1720.96 L1273.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1273.12,1720.96 1273.12,1720.96 1273.4,1720.96 1273.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1273.4 1720.76 L1273.4 1720.96 L1273.68 1720.96 L1273.68 1720.76 L1273.4 1720.76 L1273.4 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1273.4,1720.76 1273.4,1720.96 1273.68,1720.96 1273.68,1720.76 1273.4,1720.76 "/>
<path clip-path="url(#clip322)" d="M1273.68 1720.96 L1273.68 1720.96 L1273.96 1720.96 L1273.96 1720.96 L1273.68 1720.96 L1273.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1273.68,1720.96 1273.68,1720.96 1273.96,1720.96 1273.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1273.96 1720.96 L1273.96 1720.96 L1274.24 1720.96 L1274.24 1720.96 L1273.96 1720.96 L1273.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1273.96,1720.96 1273.96,1720.96 1274.24,1720.96 1273.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1274.24 1720.96 L1274.24 1720.96 L1274.52 1720.96 L1274.52 1720.96 L1274.24 1720.96 L1274.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1274.24,1720.96 1274.24,1720.96 1274.52,1720.96 1274.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1274.52 1720.96 L1274.52 1720.96 L1274.81 1720.96 L1274.81 1720.96 L1274.52 1720.96 L1274.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1274.52,1720.96 1274.52,1720.96 1274.81,1720.96 1274.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1274.81 1720.96 L1274.81 1720.96 L1275.09 1720.96 L1275.09 1720.96 L1274.81 1720.96 L1274.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1274.81,1720.96 1274.81,1720.96 1275.09,1720.96 1274.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1275.09 1720.96 L1275.09 1720.96 L1275.37 1720.96 L1275.37 1720.96 L1275.09 1720.96 L1275.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1275.09,1720.96 1275.09,1720.96 1275.37,1720.96 1275.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1275.37 1720.76 L1275.37 1720.96 L1275.65 1720.96 L1275.65 1720.76 L1275.37 1720.76 L1275.37 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1275.37,1720.76 1275.37,1720.96 1275.65,1720.96 1275.65,1720.76 1275.37,1720.76 "/>
<path clip-path="url(#clip322)" d="M1275.65 1720.96 L1275.65 1720.96 L1275.93 1720.96 L1275.93 1720.96 L1275.65 1720.96 L1275.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1275.65,1720.96 1275.65,1720.96 1275.93,1720.96 1275.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1275.93 1720.96 L1275.93 1720.96 L1276.21 1720.96 L1276.21 1720.96 L1275.93 1720.96 L1275.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1275.93,1720.96 1275.93,1720.96 1276.21,1720.96 1275.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1276.21 1720.96 L1276.21 1720.96 L1276.5 1720.96 L1276.5 1720.96 L1276.21 1720.96 L1276.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1276.21,1720.96 1276.21,1720.96 1276.5,1720.96 1276.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1276.5 1720.96 L1276.5 1720.96 L1276.78 1720.96 L1276.78 1720.96 L1276.5 1720.96 L1276.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1276.5,1720.96 1276.5,1720.96 1276.78,1720.96 1276.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1276.78 1720.96 L1276.78 1720.96 L1277.06 1720.96 L1277.06 1720.96 L1276.78 1720.96 L1276.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1276.78,1720.96 1276.78,1720.96 1277.06,1720.96 1276.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1277.06 1720.96 L1277.06 1720.96 L1277.34 1720.96 L1277.34 1720.96 L1277.06 1720.96 L1277.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1277.06,1720.96 1277.06,1720.96 1277.34,1720.96 1277.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1277.34 1720.96 L1277.34 1720.96 L1277.62 1720.96 L1277.62 1720.96 L1277.34 1720.96 L1277.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1277.34,1720.96 1277.34,1720.96 1277.62,1720.96 1277.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1277.62 1720.96 L1277.62 1720.96 L1277.91 1720.96 L1277.91 1720.96 L1277.62 1720.96 L1277.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1277.62,1720.96 1277.62,1720.96 1277.91,1720.96 1277.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1277.91 1720.96 L1277.91 1720.96 L1278.19 1720.96 L1278.19 1720.96 L1277.91 1720.96 L1277.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1277.91,1720.96 1277.91,1720.96 1278.19,1720.96 1277.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1278.19 1720.96 L1278.19 1720.96 L1278.47 1720.96 L1278.47 1720.96 L1278.19 1720.96 L1278.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1278.19,1720.96 1278.19,1720.96 1278.47,1720.96 1278.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1278.47 1720.96 L1278.47 1720.96 L1278.75 1720.96 L1278.75 1720.96 L1278.47 1720.96 L1278.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1278.47,1720.96 1278.47,1720.96 1278.75,1720.96 1278.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1278.75 1720.96 L1278.75 1720.96 L1279.03 1720.96 L1279.03 1720.96 L1278.75 1720.96 L1278.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1278.75,1720.96 1278.75,1720.96 1279.03,1720.96 1278.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1279.03 1720.96 L1279.03 1720.96 L1279.31 1720.96 L1279.31 1720.96 L1279.03 1720.96 L1279.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1279.03,1720.96 1279.03,1720.96 1279.31,1720.96 1279.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1279.31 1720.96 L1279.31 1720.96 L1279.6 1720.96 L1279.6 1720.96 L1279.31 1720.96 L1279.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1279.31,1720.96 1279.31,1720.96 1279.6,1720.96 1279.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1279.6 1720.76 L1279.6 1720.96 L1279.88 1720.96 L1279.88 1720.76 L1279.6 1720.76 L1279.6 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1279.6,1720.76 1279.6,1720.96 1279.88,1720.96 1279.88,1720.76 1279.6,1720.76 "/>
<path clip-path="url(#clip322)" d="M1279.88 1720.96 L1279.88 1720.96 L1280.16 1720.96 L1280.16 1720.96 L1279.88 1720.96 L1279.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1279.88,1720.96 1279.88,1720.96 1280.16,1720.96 1279.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1280.16 1720.96 L1280.16 1720.96 L1280.44 1720.96 L1280.44 1720.96 L1280.16 1720.96 L1280.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1280.16,1720.96 1280.16,1720.96 1280.44,1720.96 1280.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1280.44 1720.96 L1280.44 1720.96 L1280.72 1720.96 L1280.72 1720.96 L1280.44 1720.96 L1280.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1280.44,1720.96 1280.44,1720.96 1280.72,1720.96 1280.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1280.72 1720.96 L1280.72 1720.96 L1281 1720.96 L1281 1720.96 L1280.72 1720.96 L1280.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1280.72,1720.96 1280.72,1720.96 1281,1720.96 1280.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1281 1720.96 L1281 1720.96 L1281.29 1720.96 L1281.29 1720.96 L1281 1720.96 L1281 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1281,1720.96 1281,1720.96 1281.29,1720.96 1281,1720.96 "/>
<path clip-path="url(#clip322)" d="M1281.29 1720.96 L1281.29 1720.96 L1281.57 1720.96 L1281.57 1720.96 L1281.29 1720.96 L1281.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1281.29,1720.96 1281.29,1720.96 1281.57,1720.96 1281.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1281.57 1720.76 L1281.57 1720.96 L1281.85 1720.96 L1281.85 1720.76 L1281.57 1720.76 L1281.57 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1281.57,1720.76 1281.57,1720.96 1281.85,1720.96 1281.85,1720.76 1281.57,1720.76 "/>
<path clip-path="url(#clip322)" d="M1281.85 1720.96 L1281.85 1720.96 L1282.13 1720.96 L1282.13 1720.96 L1281.85 1720.96 L1281.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1281.85,1720.96 1281.85,1720.96 1282.13,1720.96 1281.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1282.13 1720.96 L1282.13 1720.96 L1282.41 1720.96 L1282.41 1720.96 L1282.13 1720.96 L1282.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1282.13,1720.96 1282.13,1720.96 1282.41,1720.96 1282.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1282.41 1720.96 L1282.41 1720.96 L1282.69 1720.96 L1282.69 1720.96 L1282.41 1720.96 L1282.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1282.41,1720.96 1282.41,1720.96 1282.69,1720.96 1282.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1282.69 1720.76 L1282.69 1720.96 L1282.98 1720.96 L1282.98 1720.76 L1282.69 1720.76 L1282.69 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1282.69,1720.76 1282.69,1720.96 1282.98,1720.96 1282.98,1720.76 1282.69,1720.76 "/>
<path clip-path="url(#clip322)" d="M1282.98 1720.96 L1282.98 1720.96 L1283.26 1720.96 L1283.26 1720.96 L1282.98 1720.96 L1282.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1282.98,1720.96 1282.98,1720.96 1283.26,1720.96 1282.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1283.26 1720.96 L1283.26 1720.96 L1283.54 1720.96 L1283.54 1720.96 L1283.26 1720.96 L1283.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1283.26,1720.96 1283.26,1720.96 1283.54,1720.96 1283.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1283.54 1720.96 L1283.54 1720.96 L1283.82 1720.96 L1283.82 1720.96 L1283.54 1720.96 L1283.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1283.54,1720.96 1283.54,1720.96 1283.82,1720.96 1283.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1283.82 1720.96 L1283.82 1720.96 L1284.1 1720.96 L1284.1 1720.96 L1283.82 1720.96 L1283.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1283.82,1720.96 1283.82,1720.96 1284.1,1720.96 1283.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1284.1 1720.96 L1284.1 1720.96 L1284.38 1720.96 L1284.38 1720.96 L1284.1 1720.96 L1284.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1284.1,1720.96 1284.1,1720.96 1284.38,1720.96 1284.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1284.38 1720.96 L1284.38 1720.96 L1284.67 1720.96 L1284.67 1720.96 L1284.38 1720.96 L1284.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1284.38,1720.96 1284.38,1720.96 1284.67,1720.96 1284.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1284.67 1720.96 L1284.67 1720.96 L1284.95 1720.96 L1284.95 1720.96 L1284.67 1720.96 L1284.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1284.67,1720.96 1284.67,1720.96 1284.95,1720.96 1284.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1284.95 1720.96 L1284.95 1720.96 L1285.23 1720.96 L1285.23 1720.96 L1284.95 1720.96 L1284.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1284.95,1720.96 1284.95,1720.96 1285.23,1720.96 1284.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1285.23 1720.96 L1285.23 1720.96 L1285.51 1720.96 L1285.51 1720.96 L1285.23 1720.96 L1285.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1285.23,1720.96 1285.23,1720.96 1285.51,1720.96 1285.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1285.51 1720.96 L1285.51 1720.96 L1285.79 1720.96 L1285.79 1720.96 L1285.51 1720.96 L1285.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1285.51,1720.96 1285.51,1720.96 1285.79,1720.96 1285.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1285.79 1720.96 L1285.79 1720.96 L1286.08 1720.96 L1286.08 1720.96 L1285.79 1720.96 L1285.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1285.79,1720.96 1285.79,1720.96 1286.08,1720.96 1285.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1286.08 1720.96 L1286.08 1720.96 L1286.36 1720.96 L1286.36 1720.96 L1286.08 1720.96 L1286.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1286.08,1720.96 1286.08,1720.96 1286.36,1720.96 1286.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1286.36 1720.96 L1286.36 1720.96 L1286.64 1720.96 L1286.64 1720.96 L1286.36 1720.96 L1286.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1286.36,1720.96 1286.36,1720.96 1286.64,1720.96 1286.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1286.64 1720.96 L1286.64 1720.96 L1286.92 1720.96 L1286.92 1720.96 L1286.64 1720.96 L1286.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1286.64,1720.96 1286.64,1720.96 1286.92,1720.96 1286.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1286.92 1720.96 L1286.92 1720.96 L1287.2 1720.96 L1287.2 1720.96 L1286.92 1720.96 L1286.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1286.92,1720.96 1286.92,1720.96 1287.2,1720.96 1286.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1287.2 1720.96 L1287.2 1720.96 L1287.48 1720.96 L1287.48 1720.96 L1287.2 1720.96 L1287.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1287.2,1720.96 1287.2,1720.96 1287.48,1720.96 1287.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1287.48 1720.76 L1287.48 1720.96 L1287.77 1720.96 L1287.77 1720.76 L1287.48 1720.76 L1287.48 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1287.48,1720.76 1287.48,1720.96 1287.77,1720.96 1287.77,1720.76 1287.48,1720.76 "/>
<path clip-path="url(#clip322)" d="M1287.77 1720.96 L1287.77 1720.96 L1288.05 1720.96 L1288.05 1720.96 L1287.77 1720.96 L1287.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1287.77,1720.96 1287.77,1720.96 1288.05,1720.96 1287.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1288.05 1720.96 L1288.05 1720.96 L1288.33 1720.96 L1288.33 1720.96 L1288.05 1720.96 L1288.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1288.05,1720.96 1288.05,1720.96 1288.33,1720.96 1288.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1288.33 1720.76 L1288.33 1720.96 L1288.61 1720.96 L1288.61 1720.76 L1288.33 1720.76 L1288.33 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1288.33,1720.76 1288.33,1720.96 1288.61,1720.96 1288.61,1720.76 1288.33,1720.76 "/>
<path clip-path="url(#clip322)" d="M1288.61 1720.96 L1288.61 1720.96 L1288.89 1720.96 L1288.89 1720.96 L1288.61 1720.96 L1288.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1288.61,1720.96 1288.61,1720.96 1288.89,1720.96 1288.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1288.89 1720.96 L1288.89 1720.96 L1289.17 1720.96 L1289.17 1720.96 L1288.89 1720.96 L1288.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1288.89,1720.96 1288.89,1720.96 1289.17,1720.96 1288.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1289.17 1720.76 L1289.17 1720.96 L1289.46 1720.96 L1289.46 1720.76 L1289.17 1720.76 L1289.17 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1289.17,1720.76 1289.17,1720.96 1289.46,1720.96 1289.46,1720.76 1289.17,1720.76 "/>
<path clip-path="url(#clip322)" d="M1289.46 1720.96 L1289.46 1720.96 L1289.74 1720.96 L1289.74 1720.96 L1289.46 1720.96 L1289.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1289.46,1720.96 1289.46,1720.96 1289.74,1720.96 1289.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1289.74 1720.96 L1289.74 1720.96 L1290.02 1720.96 L1290.02 1720.96 L1289.74 1720.96 L1289.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1289.74,1720.96 1289.74,1720.96 1290.02,1720.96 1289.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1290.02 1720.96 L1290.02 1720.96 L1290.3 1720.96 L1290.3 1720.96 L1290.02 1720.96 L1290.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1290.02,1720.96 1290.02,1720.96 1290.3,1720.96 1290.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1290.3 1720.76 L1290.3 1720.96 L1290.58 1720.96 L1290.58 1720.76 L1290.3 1720.76 L1290.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1290.3,1720.76 1290.3,1720.96 1290.58,1720.96 1290.58,1720.76 1290.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1290.58 1720.96 L1290.58 1720.96 L1290.86 1720.96 L1290.86 1720.96 L1290.58 1720.96 L1290.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1290.58,1720.96 1290.58,1720.96 1290.86,1720.96 1290.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1290.86 1720.96 L1290.86 1720.96 L1291.15 1720.96 L1291.15 1720.96 L1290.86 1720.96 L1290.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1290.86,1720.96 1290.86,1720.96 1291.15,1720.96 1290.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1291.15 1720.96 L1291.15 1720.96 L1291.43 1720.96 L1291.43 1720.96 L1291.15 1720.96 L1291.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1291.15,1720.96 1291.15,1720.96 1291.43,1720.96 1291.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1291.43 1720.96 L1291.43 1720.96 L1291.71 1720.96 L1291.71 1720.96 L1291.43 1720.96 L1291.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1291.43,1720.96 1291.43,1720.96 1291.71,1720.96 1291.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1291.71 1720.96 L1291.71 1720.96 L1291.99 1720.96 L1291.99 1720.96 L1291.71 1720.96 L1291.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1291.71,1720.96 1291.71,1720.96 1291.99,1720.96 1291.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1291.99 1720.76 L1291.99 1720.96 L1292.27 1720.96 L1292.27 1720.76 L1291.99 1720.76 L1291.99 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1291.99,1720.76 1291.99,1720.96 1292.27,1720.96 1292.27,1720.76 1291.99,1720.76 "/>
<path clip-path="url(#clip322)" d="M1292.27 1720.96 L1292.27 1720.96 L1292.55 1720.96 L1292.55 1720.96 L1292.27 1720.96 L1292.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1292.27,1720.96 1292.27,1720.96 1292.55,1720.96 1292.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1292.55 1720.96 L1292.55 1720.96 L1292.84 1720.96 L1292.84 1720.96 L1292.55 1720.96 L1292.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1292.55,1720.96 1292.55,1720.96 1292.84,1720.96 1292.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1292.84 1720.76 L1292.84 1720.96 L1293.12 1720.96 L1293.12 1720.76 L1292.84 1720.76 L1292.84 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1292.84,1720.76 1292.84,1720.96 1293.12,1720.96 1293.12,1720.76 1292.84,1720.76 "/>
<path clip-path="url(#clip322)" d="M1293.12 1720.96 L1293.12 1720.96 L1293.4 1720.96 L1293.4 1720.96 L1293.12 1720.96 L1293.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1293.12,1720.96 1293.12,1720.96 1293.4,1720.96 1293.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1293.4 1720.96 L1293.4 1720.96 L1293.68 1720.96 L1293.68 1720.96 L1293.4 1720.96 L1293.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1293.4,1720.96 1293.4,1720.96 1293.68,1720.96 1293.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1293.68 1720.96 L1293.68 1720.96 L1293.96 1720.96 L1293.96 1720.96 L1293.68 1720.96 L1293.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1293.68,1720.96 1293.68,1720.96 1293.96,1720.96 1293.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1293.96 1720.96 L1293.96 1720.96 L1294.25 1720.96 L1294.25 1720.96 L1293.96 1720.96 L1293.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1293.96,1720.96 1293.96,1720.96 1294.25,1720.96 1293.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1294.25 1720.96 L1294.25 1720.96 L1294.53 1720.96 L1294.53 1720.96 L1294.25 1720.96 L1294.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1294.25,1720.96 1294.25,1720.96 1294.53,1720.96 1294.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1294.53 1720.96 L1294.53 1720.96 L1294.81 1720.96 L1294.81 1720.96 L1294.53 1720.96 L1294.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1294.53,1720.96 1294.53,1720.96 1294.81,1720.96 1294.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1294.81 1720.96 L1294.81 1720.96 L1295.09 1720.96 L1295.09 1720.96 L1294.81 1720.96 L1294.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1294.81,1720.96 1294.81,1720.96 1295.09,1720.96 1294.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1295.09 1720.96 L1295.09 1720.96 L1295.37 1720.96 L1295.37 1720.96 L1295.09 1720.96 L1295.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1295.09,1720.96 1295.09,1720.96 1295.37,1720.96 1295.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1295.37 1720.96 L1295.37 1720.96 L1295.65 1720.96 L1295.65 1720.96 L1295.37 1720.96 L1295.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1295.37,1720.96 1295.37,1720.96 1295.65,1720.96 1295.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1295.65 1720.96 L1295.65 1720.96 L1295.94 1720.96 L1295.94 1720.96 L1295.65 1720.96 L1295.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1295.65,1720.96 1295.65,1720.96 1295.94,1720.96 1295.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1295.94 1720.96 L1295.94 1720.96 L1296.22 1720.96 L1296.22 1720.96 L1295.94 1720.96 L1295.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1295.94,1720.96 1295.94,1720.96 1296.22,1720.96 1295.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1296.22 1720.96 L1296.22 1720.96 L1296.5 1720.96 L1296.5 1720.96 L1296.22 1720.96 L1296.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1296.22,1720.96 1296.22,1720.96 1296.5,1720.96 1296.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1296.5 1720.96 L1296.5 1720.96 L1296.78 1720.96 L1296.78 1720.96 L1296.5 1720.96 L1296.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1296.5,1720.96 1296.5,1720.96 1296.78,1720.96 1296.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1296.78 1720.96 L1296.78 1720.96 L1297.06 1720.96 L1297.06 1720.96 L1296.78 1720.96 L1296.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1296.78,1720.96 1296.78,1720.96 1297.06,1720.96 1296.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1297.06 1720.96 L1297.06 1720.96 L1297.34 1720.96 L1297.34 1720.96 L1297.06 1720.96 L1297.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1297.06,1720.96 1297.06,1720.96 1297.34,1720.96 1297.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1297.34 1720.96 L1297.34 1720.96 L1297.63 1720.96 L1297.63 1720.96 L1297.34 1720.96 L1297.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1297.34,1720.96 1297.34,1720.96 1297.63,1720.96 1297.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1297.63 1720.96 L1297.63 1720.96 L1297.91 1720.96 L1297.91 1720.96 L1297.63 1720.96 L1297.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1297.63,1720.96 1297.63,1720.96 1297.91,1720.96 1297.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1297.91 1720.96 L1297.91 1720.96 L1298.19 1720.96 L1298.19 1720.96 L1297.91 1720.96 L1297.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1297.91,1720.96 1297.91,1720.96 1298.19,1720.96 1297.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1298.19 1720.96 L1298.19 1720.96 L1298.47 1720.96 L1298.47 1720.96 L1298.19 1720.96 L1298.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1298.19,1720.96 1298.19,1720.96 1298.47,1720.96 1298.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1298.47 1720.76 L1298.47 1720.96 L1298.75 1720.96 L1298.75 1720.76 L1298.47 1720.76 L1298.47 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1298.47,1720.76 1298.47,1720.96 1298.75,1720.96 1298.75,1720.76 1298.47,1720.76 "/>
<path clip-path="url(#clip322)" d="M1298.75 1720.96 L1298.75 1720.96 L1299.03 1720.96 L1299.03 1720.96 L1298.75 1720.96 L1298.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1298.75,1720.96 1298.75,1720.96 1299.03,1720.96 1298.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1299.03 1720.96 L1299.03 1720.96 L1299.32 1720.96 L1299.32 1720.96 L1299.03 1720.96 L1299.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1299.03,1720.96 1299.03,1720.96 1299.32,1720.96 1299.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1299.32 1720.96 L1299.32 1720.96 L1299.6 1720.96 L1299.6 1720.96 L1299.32 1720.96 L1299.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1299.32,1720.96 1299.32,1720.96 1299.6,1720.96 1299.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1299.6 1720.56 L1299.6 1720.96 L1299.88 1720.96 L1299.88 1720.56 L1299.6 1720.56 L1299.6 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1299.6,1720.56 1299.6,1720.96 1299.88,1720.96 1299.88,1720.56 1299.6,1720.56 "/>
<path clip-path="url(#clip322)" d="M1299.88 1720.96 L1299.88 1720.96 L1300.16 1720.96 L1300.16 1720.96 L1299.88 1720.96 L1299.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1299.88,1720.96 1299.88,1720.96 1300.16,1720.96 1299.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1300.16 1720.96 L1300.16 1720.96 L1300.44 1720.96 L1300.44 1720.96 L1300.16 1720.96 L1300.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1300.16,1720.96 1300.16,1720.96 1300.44,1720.96 1300.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1300.44 1720.96 L1300.44 1720.96 L1300.72 1720.96 L1300.72 1720.96 L1300.44 1720.96 L1300.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1300.44,1720.96 1300.44,1720.96 1300.72,1720.96 1300.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1300.72 1720.96 L1300.72 1720.96 L1301.01 1720.96 L1301.01 1720.96 L1300.72 1720.96 L1300.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1300.72,1720.96 1300.72,1720.96 1301.01,1720.96 1300.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1301.01 1720.96 L1301.01 1720.96 L1301.29 1720.96 L1301.29 1720.96 L1301.01 1720.96 L1301.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1301.01,1720.96 1301.01,1720.96 1301.29,1720.96 1301.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1301.29 1720.96 L1301.29 1720.96 L1301.57 1720.96 L1301.57 1720.96 L1301.29 1720.96 L1301.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1301.29,1720.96 1301.29,1720.96 1301.57,1720.96 1301.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1301.57 1720.96 L1301.57 1720.96 L1301.85 1720.96 L1301.85 1720.96 L1301.57 1720.96 L1301.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1301.57,1720.96 1301.57,1720.96 1301.85,1720.96 1301.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1301.85 1720.96 L1301.85 1720.96 L1302.13 1720.96 L1302.13 1720.96 L1301.85 1720.96 L1301.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1301.85,1720.96 1301.85,1720.96 1302.13,1720.96 1301.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1302.13 1720.96 L1302.13 1720.96 L1302.42 1720.96 L1302.42 1720.96 L1302.13 1720.96 L1302.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1302.13,1720.96 1302.13,1720.96 1302.42,1720.96 1302.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1302.42 1720.96 L1302.42 1720.96 L1302.7 1720.96 L1302.7 1720.96 L1302.42 1720.96 L1302.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1302.42,1720.96 1302.42,1720.96 1302.7,1720.96 1302.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1302.7 1720.96 L1302.7 1720.96 L1302.98 1720.96 L1302.98 1720.96 L1302.7 1720.96 L1302.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1302.7,1720.96 1302.7,1720.96 1302.98,1720.96 1302.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1302.98 1720.76 L1302.98 1720.96 L1303.26 1720.96 L1303.26 1720.76 L1302.98 1720.76 L1302.98 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1302.98,1720.76 1302.98,1720.96 1303.26,1720.96 1303.26,1720.76 1302.98,1720.76 "/>
<path clip-path="url(#clip322)" d="M1303.26 1720.96 L1303.26 1720.96 L1303.54 1720.96 L1303.54 1720.96 L1303.26 1720.96 L1303.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1303.26,1720.96 1303.26,1720.96 1303.54,1720.96 1303.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1303.54 1720.96 L1303.54 1720.96 L1303.82 1720.96 L1303.82 1720.96 L1303.54 1720.96 L1303.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1303.54,1720.96 1303.54,1720.96 1303.82,1720.96 1303.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1303.82 1720.96 L1303.82 1720.96 L1304.11 1720.96 L1304.11 1720.96 L1303.82 1720.96 L1303.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1303.82,1720.96 1303.82,1720.96 1304.11,1720.96 1303.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1304.11 1720.96 L1304.11 1720.96 L1304.39 1720.96 L1304.39 1720.96 L1304.11 1720.96 L1304.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1304.11,1720.96 1304.11,1720.96 1304.39,1720.96 1304.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1304.39 1720.96 L1304.39 1720.96 L1304.67 1720.96 L1304.67 1720.96 L1304.39 1720.96 L1304.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1304.39,1720.96 1304.39,1720.96 1304.67,1720.96 1304.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1304.67 1720.96 L1304.67 1720.96 L1304.95 1720.96 L1304.95 1720.96 L1304.67 1720.96 L1304.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1304.67,1720.96 1304.67,1720.96 1304.95,1720.96 1304.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1304.95 1720.96 L1304.95 1720.96 L1305.23 1720.96 L1305.23 1720.96 L1304.95 1720.96 L1304.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1304.95,1720.96 1304.95,1720.96 1305.23,1720.96 1304.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1305.23 1720.76 L1305.23 1720.96 L1305.51 1720.96 L1305.51 1720.76 L1305.23 1720.76 L1305.23 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1305.23,1720.76 1305.23,1720.96 1305.51,1720.96 1305.51,1720.76 1305.23,1720.76 "/>
<path clip-path="url(#clip322)" d="M1305.51 1720.96 L1305.51 1720.96 L1305.8 1720.96 L1305.8 1720.96 L1305.51 1720.96 L1305.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1305.51,1720.96 1305.51,1720.96 1305.8,1720.96 1305.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1305.8 1720.96 L1305.8 1720.96 L1306.08 1720.96 L1306.08 1720.96 L1305.8 1720.96 L1305.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1305.8,1720.96 1305.8,1720.96 1306.08,1720.96 1305.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1306.08 1720.96 L1306.08 1720.96 L1306.36 1720.96 L1306.36 1720.96 L1306.08 1720.96 L1306.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1306.08,1720.96 1306.08,1720.96 1306.36,1720.96 1306.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1306.36 1720.96 L1306.36 1720.96 L1306.64 1720.96 L1306.64 1720.96 L1306.36 1720.96 L1306.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1306.36,1720.96 1306.36,1720.96 1306.64,1720.96 1306.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1306.64 1720.96 L1306.64 1720.96 L1306.92 1720.96 L1306.92 1720.96 L1306.64 1720.96 L1306.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1306.64,1720.96 1306.64,1720.96 1306.92,1720.96 1306.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1306.92 1720.96 L1306.92 1720.96 L1307.2 1720.96 L1307.2 1720.96 L1306.92 1720.96 L1306.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1306.92,1720.96 1306.92,1720.96 1307.2,1720.96 1306.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1307.2 1720.96 L1307.2 1720.96 L1307.49 1720.96 L1307.49 1720.96 L1307.2 1720.96 L1307.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1307.2,1720.96 1307.2,1720.96 1307.49,1720.96 1307.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1307.49 1720.96 L1307.49 1720.96 L1307.77 1720.96 L1307.77 1720.96 L1307.49 1720.96 L1307.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1307.49,1720.96 1307.49,1720.96 1307.77,1720.96 1307.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1307.77 1720.96 L1307.77 1720.96 L1308.05 1720.96 L1308.05 1720.96 L1307.77 1720.96 L1307.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1307.77,1720.96 1307.77,1720.96 1308.05,1720.96 1307.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1308.05 1720.96 L1308.05 1720.96 L1308.33 1720.96 L1308.33 1720.96 L1308.05 1720.96 L1308.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1308.05,1720.96 1308.05,1720.96 1308.33,1720.96 1308.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1308.33 1720.96 L1308.33 1720.96 L1308.61 1720.96 L1308.61 1720.96 L1308.33 1720.96 L1308.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1308.33,1720.96 1308.33,1720.96 1308.61,1720.96 1308.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1308.61 1720.96 L1308.61 1720.96 L1308.89 1720.96 L1308.89 1720.96 L1308.61 1720.96 L1308.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1308.61,1720.96 1308.61,1720.96 1308.89,1720.96 1308.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1308.89 1720.96 L1308.89 1720.96 L1309.18 1720.96 L1309.18 1720.96 L1308.89 1720.96 L1308.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1308.89,1720.96 1308.89,1720.96 1309.18,1720.96 1308.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1309.18 1720.76 L1309.18 1720.96 L1309.46 1720.96 L1309.46 1720.76 L1309.18 1720.76 L1309.18 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1309.18,1720.76 1309.18,1720.96 1309.46,1720.96 1309.46,1720.76 1309.18,1720.76 "/>
<path clip-path="url(#clip322)" d="M1309.46 1720.76 L1309.46 1720.96 L1309.74 1720.96 L1309.74 1720.76 L1309.46 1720.76 L1309.46 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1309.46,1720.76 1309.46,1720.96 1309.74,1720.96 1309.74,1720.76 1309.46,1720.76 "/>
<path clip-path="url(#clip322)" d="M1309.74 1720.96 L1309.74 1720.96 L1310.02 1720.96 L1310.02 1720.96 L1309.74 1720.96 L1309.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1309.74,1720.96 1309.74,1720.96 1310.02,1720.96 1309.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1310.02 1720.96 L1310.02 1720.96 L1310.3 1720.96 L1310.3 1720.96 L1310.02 1720.96 L1310.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1310.02,1720.96 1310.02,1720.96 1310.3,1720.96 1310.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1310.3 1720.96 L1310.3 1720.96 L1310.59 1720.96 L1310.59 1720.96 L1310.3 1720.96 L1310.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1310.3,1720.96 1310.3,1720.96 1310.59,1720.96 1310.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1310.59 1720.96 L1310.59 1720.96 L1310.87 1720.96 L1310.87 1720.96 L1310.59 1720.96 L1310.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1310.59,1720.96 1310.59,1720.96 1310.87,1720.96 1310.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1310.87 1720.96 L1310.87 1720.96 L1311.15 1720.96 L1311.15 1720.96 L1310.87 1720.96 L1310.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1310.87,1720.96 1310.87,1720.96 1311.15,1720.96 1310.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1311.15 1720.96 L1311.15 1720.96 L1311.43 1720.96 L1311.43 1720.96 L1311.15 1720.96 L1311.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1311.15,1720.96 1311.15,1720.96 1311.43,1720.96 1311.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1311.43 1720.96 L1311.43 1720.96 L1311.71 1720.96 L1311.71 1720.96 L1311.43 1720.96 L1311.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1311.43,1720.96 1311.43,1720.96 1311.71,1720.96 1311.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1311.71 1720.96 L1311.71 1720.96 L1311.99 1720.96 L1311.99 1720.96 L1311.71 1720.96 L1311.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1311.71,1720.96 1311.71,1720.96 1311.99,1720.96 1311.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1311.99 1720.96 L1311.99 1720.96 L1312.28 1720.96 L1312.28 1720.96 L1311.99 1720.96 L1311.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1311.99,1720.96 1311.99,1720.96 1312.28,1720.96 1311.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1312.28 1720.96 L1312.28 1720.96 L1312.56 1720.96 L1312.56 1720.96 L1312.28 1720.96 L1312.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1312.28,1720.96 1312.28,1720.96 1312.56,1720.96 1312.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1312.56 1720.96 L1312.56 1720.96 L1312.84 1720.96 L1312.84 1720.96 L1312.56 1720.96 L1312.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1312.56,1720.96 1312.56,1720.96 1312.84,1720.96 1312.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1312.84 1720.96 L1312.84 1720.96 L1313.12 1720.96 L1313.12 1720.96 L1312.84 1720.96 L1312.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1312.84,1720.96 1312.84,1720.96 1313.12,1720.96 1312.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1313.12 1720.96 L1313.12 1720.96 L1313.4 1720.96 L1313.4 1720.96 L1313.12 1720.96 L1313.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1313.12,1720.96 1313.12,1720.96 1313.4,1720.96 1313.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1313.4 1720.96 L1313.4 1720.96 L1313.68 1720.96 L1313.68 1720.96 L1313.4 1720.96 L1313.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1313.4,1720.96 1313.4,1720.96 1313.68,1720.96 1313.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1313.68 1720.96 L1313.68 1720.96 L1313.97 1720.96 L1313.97 1720.96 L1313.68 1720.96 L1313.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1313.68,1720.96 1313.68,1720.96 1313.97,1720.96 1313.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1313.97 1720.96 L1313.97 1720.96 L1314.25 1720.96 L1314.25 1720.96 L1313.97 1720.96 L1313.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1313.97,1720.96 1313.97,1720.96 1314.25,1720.96 1313.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1314.25 1720.96 L1314.25 1720.96 L1314.53 1720.96 L1314.53 1720.96 L1314.25 1720.96 L1314.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1314.25,1720.96 1314.25,1720.96 1314.53,1720.96 1314.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1314.53 1720.96 L1314.53 1720.96 L1314.81 1720.96 L1314.81 1720.96 L1314.53 1720.96 L1314.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1314.53,1720.96 1314.53,1720.96 1314.81,1720.96 1314.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1314.81 1720.96 L1314.81 1720.96 L1315.09 1720.96 L1315.09 1720.96 L1314.81 1720.96 L1314.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1314.81,1720.96 1314.81,1720.96 1315.09,1720.96 1314.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1315.09 1720.96 L1315.09 1720.96 L1315.37 1720.96 L1315.37 1720.96 L1315.09 1720.96 L1315.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1315.09,1720.96 1315.09,1720.96 1315.37,1720.96 1315.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1315.37 1720.96 L1315.37 1720.96 L1315.66 1720.96 L1315.66 1720.96 L1315.37 1720.96 L1315.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1315.37,1720.96 1315.37,1720.96 1315.66,1720.96 1315.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1315.66 1720.96 L1315.66 1720.96 L1315.94 1720.96 L1315.94 1720.96 L1315.66 1720.96 L1315.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1315.66,1720.96 1315.66,1720.96 1315.94,1720.96 1315.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1315.94 1720.96 L1315.94 1720.96 L1316.22 1720.96 L1316.22 1720.96 L1315.94 1720.96 L1315.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1315.94,1720.96 1315.94,1720.96 1316.22,1720.96 1315.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1316.22 1720.96 L1316.22 1720.96 L1316.5 1720.96 L1316.5 1720.96 L1316.22 1720.96 L1316.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1316.22,1720.96 1316.22,1720.96 1316.5,1720.96 1316.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1316.5 1720.96 L1316.5 1720.96 L1316.78 1720.96 L1316.78 1720.96 L1316.5 1720.96 L1316.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1316.5,1720.96 1316.5,1720.96 1316.78,1720.96 1316.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1316.78 1720.96 L1316.78 1720.96 L1317.07 1720.96 L1317.07 1720.96 L1316.78 1720.96 L1316.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1316.78,1720.96 1316.78,1720.96 1317.07,1720.96 1316.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1317.07 1720.56 L1317.07 1720.96 L1317.35 1720.96 L1317.35 1720.56 L1317.07 1720.56 L1317.07 1720.56  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1317.07,1720.56 1317.07,1720.96 1317.35,1720.96 1317.35,1720.56 1317.07,1720.56 "/>
<path clip-path="url(#clip322)" d="M1317.35 1720.96 L1317.35 1720.96 L1317.63 1720.96 L1317.63 1720.96 L1317.35 1720.96 L1317.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1317.35,1720.96 1317.35,1720.96 1317.63,1720.96 1317.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1317.63 1720.96 L1317.63 1720.96 L1317.91 1720.96 L1317.91 1720.96 L1317.63 1720.96 L1317.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1317.63,1720.96 1317.63,1720.96 1317.91,1720.96 1317.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1317.91 1720.96 L1317.91 1720.96 L1318.19 1720.96 L1318.19 1720.96 L1317.91 1720.96 L1317.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1317.91,1720.96 1317.91,1720.96 1318.19,1720.96 1317.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1318.19 1720.76 L1318.19 1720.96 L1318.47 1720.96 L1318.47 1720.76 L1318.19 1720.76 L1318.19 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1318.19,1720.76 1318.19,1720.96 1318.47,1720.96 1318.47,1720.76 1318.19,1720.76 "/>
<path clip-path="url(#clip322)" d="M1318.47 1720.96 L1318.47 1720.96 L1318.76 1720.96 L1318.76 1720.96 L1318.47 1720.96 L1318.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1318.47,1720.96 1318.47,1720.96 1318.76,1720.96 1318.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1318.76 1720.96 L1318.76 1720.96 L1319.04 1720.96 L1319.04 1720.96 L1318.76 1720.96 L1318.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1318.76,1720.96 1318.76,1720.96 1319.04,1720.96 1318.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1319.04 1720.76 L1319.04 1720.96 L1319.32 1720.96 L1319.32 1720.76 L1319.04 1720.76 L1319.04 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1319.04,1720.76 1319.04,1720.96 1319.32,1720.96 1319.32,1720.76 1319.04,1720.76 "/>
<path clip-path="url(#clip322)" d="M1319.32 1720.96 L1319.32 1720.96 L1319.6 1720.96 L1319.6 1720.96 L1319.32 1720.96 L1319.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1319.32,1720.96 1319.32,1720.96 1319.6,1720.96 1319.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1319.6 1720.96 L1319.6 1720.96 L1319.88 1720.96 L1319.88 1720.96 L1319.6 1720.96 L1319.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1319.6,1720.96 1319.6,1720.96 1319.88,1720.96 1319.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1319.88 1720.96 L1319.88 1720.96 L1320.16 1720.96 L1320.16 1720.96 L1319.88 1720.96 L1319.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1319.88,1720.96 1319.88,1720.96 1320.16,1720.96 1319.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1320.16 1720.96 L1320.16 1720.96 L1320.45 1720.96 L1320.45 1720.96 L1320.16 1720.96 L1320.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1320.16,1720.96 1320.16,1720.96 1320.45,1720.96 1320.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1320.45 1720.96 L1320.45 1720.96 L1320.73 1720.96 L1320.73 1720.96 L1320.45 1720.96 L1320.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1320.45,1720.96 1320.45,1720.96 1320.73,1720.96 1320.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1320.73 1720.96 L1320.73 1720.96 L1321.01 1720.96 L1321.01 1720.96 L1320.73 1720.96 L1320.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1320.73,1720.96 1320.73,1720.96 1321.01,1720.96 1320.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1321.01 1720.96 L1321.01 1720.96 L1321.29 1720.96 L1321.29 1720.96 L1321.01 1720.96 L1321.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1321.01,1720.96 1321.01,1720.96 1321.29,1720.96 1321.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1321.29 1720.96 L1321.29 1720.96 L1321.57 1720.96 L1321.57 1720.96 L1321.29 1720.96 L1321.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1321.29,1720.96 1321.29,1720.96 1321.57,1720.96 1321.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1321.57 1720.96 L1321.57 1720.96 L1321.85 1720.96 L1321.85 1720.96 L1321.57 1720.96 L1321.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1321.57,1720.96 1321.57,1720.96 1321.85,1720.96 1321.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1321.85 1720.96 L1321.85 1720.96 L1322.14 1720.96 L1322.14 1720.96 L1321.85 1720.96 L1321.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1321.85,1720.96 1321.85,1720.96 1322.14,1720.96 1321.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1322.14 1720.96 L1322.14 1720.96 L1322.42 1720.96 L1322.42 1720.96 L1322.14 1720.96 L1322.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1322.14,1720.96 1322.14,1720.96 1322.42,1720.96 1322.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1322.42 1720.96 L1322.42 1720.96 L1322.7 1720.96 L1322.7 1720.96 L1322.42 1720.96 L1322.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1322.42,1720.96 1322.42,1720.96 1322.7,1720.96 1322.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1322.7 1720.96 L1322.7 1720.96 L1322.98 1720.96 L1322.98 1720.96 L1322.7 1720.96 L1322.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1322.7,1720.96 1322.7,1720.96 1322.98,1720.96 1322.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1322.98 1720.96 L1322.98 1720.96 L1323.26 1720.96 L1323.26 1720.96 L1322.98 1720.96 L1322.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1322.98,1720.96 1322.98,1720.96 1323.26,1720.96 1322.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1323.26 1720.96 L1323.26 1720.96 L1323.54 1720.96 L1323.54 1720.96 L1323.26 1720.96 L1323.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1323.26,1720.96 1323.26,1720.96 1323.54,1720.96 1323.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1323.54 1720.96 L1323.54 1720.96 L1323.83 1720.96 L1323.83 1720.96 L1323.54 1720.96 L1323.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1323.54,1720.96 1323.54,1720.96 1323.83,1720.96 1323.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1323.83 1720.96 L1323.83 1720.96 L1324.11 1720.96 L1324.11 1720.96 L1323.83 1720.96 L1323.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1323.83,1720.96 1323.83,1720.96 1324.11,1720.96 1323.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1324.11 1720.76 L1324.11 1720.96 L1324.39 1720.96 L1324.39 1720.76 L1324.11 1720.76 L1324.11 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1324.11,1720.76 1324.11,1720.96 1324.39,1720.96 1324.39,1720.76 1324.11,1720.76 "/>
<path clip-path="url(#clip322)" d="M1324.39 1720.96 L1324.39 1720.96 L1324.67 1720.96 L1324.67 1720.96 L1324.39 1720.96 L1324.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1324.39,1720.96 1324.39,1720.96 1324.67,1720.96 1324.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1324.67 1720.76 L1324.67 1720.96 L1324.95 1720.96 L1324.95 1720.76 L1324.67 1720.76 L1324.67 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1324.67,1720.76 1324.67,1720.96 1324.95,1720.96 1324.95,1720.76 1324.67,1720.76 "/>
<path clip-path="url(#clip322)" d="M1324.95 1720.96 L1324.95 1720.96 L1325.24 1720.96 L1325.24 1720.96 L1324.95 1720.96 L1324.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1324.95,1720.96 1324.95,1720.96 1325.24,1720.96 1324.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1325.24 1720.96 L1325.24 1720.96 L1325.52 1720.96 L1325.52 1720.96 L1325.24 1720.96 L1325.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1325.24,1720.96 1325.24,1720.96 1325.52,1720.96 1325.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1325.52 1720.96 L1325.52 1720.96 L1325.8 1720.96 L1325.8 1720.96 L1325.52 1720.96 L1325.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1325.52,1720.96 1325.52,1720.96 1325.8,1720.96 1325.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1325.8 1720.96 L1325.8 1720.96 L1326.08 1720.96 L1326.08 1720.96 L1325.8 1720.96 L1325.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1325.8,1720.96 1325.8,1720.96 1326.08,1720.96 1325.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1326.08 1720.96 L1326.08 1720.96 L1326.36 1720.96 L1326.36 1720.96 L1326.08 1720.96 L1326.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1326.08,1720.96 1326.08,1720.96 1326.36,1720.96 1326.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1326.36 1720.96 L1326.36 1720.96 L1326.64 1720.96 L1326.64 1720.96 L1326.36 1720.96 L1326.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1326.36,1720.96 1326.36,1720.96 1326.64,1720.96 1326.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1326.64 1720.76 L1326.64 1720.96 L1326.93 1720.96 L1326.93 1720.76 L1326.64 1720.76 L1326.64 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1326.64,1720.76 1326.64,1720.96 1326.93,1720.96 1326.93,1720.76 1326.64,1720.76 "/>
<path clip-path="url(#clip322)" d="M1326.93 1720.96 L1326.93 1720.96 L1327.21 1720.96 L1327.21 1720.96 L1326.93 1720.96 L1326.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1326.93,1720.96 1326.93,1720.96 1327.21,1720.96 1326.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1327.21 1720.96 L1327.21 1720.96 L1327.49 1720.96 L1327.49 1720.96 L1327.21 1720.96 L1327.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1327.21,1720.96 1327.21,1720.96 1327.49,1720.96 1327.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1327.49 1720.96 L1327.49 1720.96 L1327.77 1720.96 L1327.77 1720.96 L1327.49 1720.96 L1327.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1327.49,1720.96 1327.49,1720.96 1327.77,1720.96 1327.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1327.77 1720.96 L1327.77 1720.96 L1328.05 1720.96 L1328.05 1720.96 L1327.77 1720.96 L1327.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1327.77,1720.96 1327.77,1720.96 1328.05,1720.96 1327.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1328.05 1720.96 L1328.05 1720.96 L1328.33 1720.96 L1328.33 1720.96 L1328.05 1720.96 L1328.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1328.05,1720.96 1328.05,1720.96 1328.33,1720.96 1328.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1328.33 1720.76 L1328.33 1720.96 L1328.62 1720.96 L1328.62 1720.76 L1328.33 1720.76 L1328.33 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1328.33,1720.76 1328.33,1720.96 1328.62,1720.96 1328.62,1720.76 1328.33,1720.76 "/>
<path clip-path="url(#clip322)" d="M1328.62 1720.96 L1328.62 1720.96 L1328.9 1720.96 L1328.9 1720.96 L1328.62 1720.96 L1328.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1328.62,1720.96 1328.62,1720.96 1328.9,1720.96 1328.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1328.9 1720.96 L1328.9 1720.96 L1329.18 1720.96 L1329.18 1720.96 L1328.9 1720.96 L1328.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1328.9,1720.96 1328.9,1720.96 1329.18,1720.96 1328.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1329.18 1720.96 L1329.18 1720.96 L1329.46 1720.96 L1329.46 1720.96 L1329.18 1720.96 L1329.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1329.18,1720.96 1329.18,1720.96 1329.46,1720.96 1329.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1329.46 1720.96 L1329.46 1720.96 L1329.74 1720.96 L1329.74 1720.96 L1329.46 1720.96 L1329.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1329.46,1720.96 1329.46,1720.96 1329.74,1720.96 1329.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1329.74 1720.96 L1329.74 1720.96 L1330.02 1720.96 L1330.02 1720.96 L1329.74 1720.96 L1329.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1329.74,1720.96 1329.74,1720.96 1330.02,1720.96 1329.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1330.02 1720.96 L1330.02 1720.96 L1330.31 1720.96 L1330.31 1720.96 L1330.02 1720.96 L1330.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1330.02,1720.96 1330.02,1720.96 1330.31,1720.96 1330.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1330.31 1720.96 L1330.31 1720.96 L1330.59 1720.96 L1330.59 1720.96 L1330.31 1720.96 L1330.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1330.31,1720.96 1330.31,1720.96 1330.59,1720.96 1330.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1330.59 1720.96 L1330.59 1720.96 L1330.87 1720.96 L1330.87 1720.96 L1330.59 1720.96 L1330.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1330.59,1720.96 1330.59,1720.96 1330.87,1720.96 1330.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1330.87 1720.96 L1330.87 1720.96 L1331.15 1720.96 L1331.15 1720.96 L1330.87 1720.96 L1330.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1330.87,1720.96 1330.87,1720.96 1331.15,1720.96 1330.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1331.15 1720.96 L1331.15 1720.96 L1331.43 1720.96 L1331.43 1720.96 L1331.15 1720.96 L1331.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1331.15,1720.96 1331.15,1720.96 1331.43,1720.96 1331.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1331.43 1720.96 L1331.43 1720.96 L1331.71 1720.96 L1331.71 1720.96 L1331.43 1720.96 L1331.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1331.43,1720.96 1331.43,1720.96 1331.71,1720.96 1331.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1331.71 1720.96 L1331.71 1720.96 L1332 1720.96 L1332 1720.96 L1331.71 1720.96 L1331.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1331.71,1720.96 1331.71,1720.96 1332,1720.96 1331.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1332 1720.96 L1332 1720.96 L1332.28 1720.96 L1332.28 1720.96 L1332 1720.96 L1332 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1332,1720.96 1332,1720.96 1332.28,1720.96 1332,1720.96 "/>
<path clip-path="url(#clip322)" d="M1332.28 1720.96 L1332.28 1720.96 L1332.56 1720.96 L1332.56 1720.96 L1332.28 1720.96 L1332.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1332.28,1720.96 1332.28,1720.96 1332.56,1720.96 1332.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1332.56 1720.96 L1332.56 1720.96 L1332.84 1720.96 L1332.84 1720.96 L1332.56 1720.96 L1332.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1332.56,1720.96 1332.56,1720.96 1332.84,1720.96 1332.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1332.84 1720.96 L1332.84 1720.96 L1333.12 1720.96 L1333.12 1720.96 L1332.84 1720.96 L1332.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1332.84,1720.96 1332.84,1720.96 1333.12,1720.96 1332.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1333.12 1720.96 L1333.12 1720.96 L1333.41 1720.96 L1333.41 1720.96 L1333.12 1720.96 L1333.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1333.12,1720.96 1333.12,1720.96 1333.41,1720.96 1333.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1333.41 1720.96 L1333.41 1720.96 L1333.69 1720.96 L1333.69 1720.96 L1333.41 1720.96 L1333.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1333.41,1720.96 1333.41,1720.96 1333.69,1720.96 1333.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1333.69 1720.96 L1333.69 1720.96 L1333.97 1720.96 L1333.97 1720.96 L1333.69 1720.96 L1333.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1333.69,1720.96 1333.69,1720.96 1333.97,1720.96 1333.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1333.97 1720.96 L1333.97 1720.96 L1334.25 1720.96 L1334.25 1720.96 L1333.97 1720.96 L1333.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1333.97,1720.96 1333.97,1720.96 1334.25,1720.96 1333.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1334.25 1720.96 L1334.25 1720.96 L1334.53 1720.96 L1334.53 1720.96 L1334.25 1720.96 L1334.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1334.25,1720.96 1334.25,1720.96 1334.53,1720.96 1334.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1334.53 1720.76 L1334.53 1720.96 L1334.81 1720.96 L1334.81 1720.76 L1334.53 1720.76 L1334.53 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1334.53,1720.76 1334.53,1720.96 1334.81,1720.96 1334.81,1720.76 1334.53,1720.76 "/>
<path clip-path="url(#clip322)" d="M1334.81 1720.96 L1334.81 1720.96 L1335.1 1720.96 L1335.1 1720.96 L1334.81 1720.96 L1334.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1334.81,1720.96 1334.81,1720.96 1335.1,1720.96 1334.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1335.1 1720.96 L1335.1 1720.96 L1335.38 1720.96 L1335.38 1720.96 L1335.1 1720.96 L1335.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1335.1,1720.96 1335.1,1720.96 1335.38,1720.96 1335.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1335.38 1720.96 L1335.38 1720.96 L1335.66 1720.96 L1335.66 1720.96 L1335.38 1720.96 L1335.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1335.38,1720.96 1335.38,1720.96 1335.66,1720.96 1335.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1335.66 1720.96 L1335.66 1720.96 L1335.94 1720.96 L1335.94 1720.96 L1335.66 1720.96 L1335.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1335.66,1720.96 1335.66,1720.96 1335.94,1720.96 1335.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1335.94 1720.96 L1335.94 1720.96 L1336.22 1720.96 L1336.22 1720.96 L1335.94 1720.96 L1335.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1335.94,1720.96 1335.94,1720.96 1336.22,1720.96 1335.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1336.22 1720.96 L1336.22 1720.96 L1336.5 1720.96 L1336.5 1720.96 L1336.22 1720.96 L1336.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1336.22,1720.96 1336.22,1720.96 1336.5,1720.96 1336.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1336.5 1720.96 L1336.5 1720.96 L1336.79 1720.96 L1336.79 1720.96 L1336.5 1720.96 L1336.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1336.5,1720.96 1336.5,1720.96 1336.79,1720.96 1336.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1336.79 1720.96 L1336.79 1720.96 L1337.07 1720.96 L1337.07 1720.96 L1336.79 1720.96 L1336.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1336.79,1720.96 1336.79,1720.96 1337.07,1720.96 1336.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1337.07 1720.96 L1337.07 1720.96 L1337.35 1720.96 L1337.35 1720.96 L1337.07 1720.96 L1337.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1337.07,1720.96 1337.07,1720.96 1337.35,1720.96 1337.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1337.35 1720.96 L1337.35 1720.96 L1337.63 1720.96 L1337.63 1720.96 L1337.35 1720.96 L1337.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1337.35,1720.96 1337.35,1720.96 1337.63,1720.96 1337.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1337.63 1720.96 L1337.63 1720.96 L1337.91 1720.96 L1337.91 1720.96 L1337.63 1720.96 L1337.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1337.63,1720.96 1337.63,1720.96 1337.91,1720.96 1337.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1337.91 1720.96 L1337.91 1720.96 L1338.19 1720.96 L1338.19 1720.96 L1337.91 1720.96 L1337.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1337.91,1720.96 1337.91,1720.96 1338.19,1720.96 1337.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1338.19 1720.96 L1338.19 1720.96 L1338.48 1720.96 L1338.48 1720.96 L1338.19 1720.96 L1338.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1338.19,1720.96 1338.19,1720.96 1338.48,1720.96 1338.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1338.48 1720.96 L1338.48 1720.96 L1338.76 1720.96 L1338.76 1720.96 L1338.48 1720.96 L1338.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1338.48,1720.96 1338.48,1720.96 1338.76,1720.96 1338.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1338.76 1720.96 L1338.76 1720.96 L1339.04 1720.96 L1339.04 1720.96 L1338.76 1720.96 L1338.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1338.76,1720.96 1338.76,1720.96 1339.04,1720.96 1338.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1339.04 1720.96 L1339.04 1720.96 L1339.32 1720.96 L1339.32 1720.96 L1339.04 1720.96 L1339.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1339.04,1720.96 1339.04,1720.96 1339.32,1720.96 1339.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1339.32 1720.96 L1339.32 1720.96 L1339.6 1720.96 L1339.6 1720.96 L1339.32 1720.96 L1339.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1339.32,1720.96 1339.32,1720.96 1339.6,1720.96 1339.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1339.6 1720.96 L1339.6 1720.96 L1339.88 1720.96 L1339.88 1720.96 L1339.6 1720.96 L1339.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1339.6,1720.96 1339.6,1720.96 1339.88,1720.96 1339.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1339.88 1720.96 L1339.88 1720.96 L1340.17 1720.96 L1340.17 1720.96 L1339.88 1720.96 L1339.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1339.88,1720.96 1339.88,1720.96 1340.17,1720.96 1339.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1340.17 1720.96 L1340.17 1720.96 L1340.45 1720.96 L1340.45 1720.96 L1340.17 1720.96 L1340.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1340.17,1720.96 1340.17,1720.96 1340.45,1720.96 1340.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1340.45 1720.96 L1340.45 1720.96 L1340.73 1720.96 L1340.73 1720.96 L1340.45 1720.96 L1340.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1340.45,1720.96 1340.45,1720.96 1340.73,1720.96 1340.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1340.73 1720.96 L1340.73 1720.96 L1341.01 1720.96 L1341.01 1720.96 L1340.73 1720.96 L1340.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1340.73,1720.96 1340.73,1720.96 1341.01,1720.96 1340.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1341.01 1720.96 L1341.01 1720.96 L1341.29 1720.96 L1341.29 1720.96 L1341.01 1720.96 L1341.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1341.01,1720.96 1341.01,1720.96 1341.29,1720.96 1341.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1341.29 1720.96 L1341.29 1720.96 L1341.58 1720.96 L1341.58 1720.96 L1341.29 1720.96 L1341.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1341.29,1720.96 1341.29,1720.96 1341.58,1720.96 1341.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1341.58 1720.96 L1341.58 1720.96 L1341.86 1720.96 L1341.86 1720.96 L1341.58 1720.96 L1341.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1341.58,1720.96 1341.58,1720.96 1341.86,1720.96 1341.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1341.86 1720.96 L1341.86 1720.96 L1342.14 1720.96 L1342.14 1720.96 L1341.86 1720.96 L1341.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1341.86,1720.96 1341.86,1720.96 1342.14,1720.96 1341.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1342.14 1720.76 L1342.14 1720.96 L1342.42 1720.96 L1342.42 1720.76 L1342.14 1720.76 L1342.14 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1342.14,1720.76 1342.14,1720.96 1342.42,1720.96 1342.42,1720.76 1342.14,1720.76 "/>
<path clip-path="url(#clip322)" d="M1342.42 1720.96 L1342.42 1720.96 L1342.7 1720.96 L1342.7 1720.96 L1342.42 1720.96 L1342.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1342.42,1720.96 1342.42,1720.96 1342.7,1720.96 1342.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1342.7 1720.96 L1342.7 1720.96 L1342.98 1720.96 L1342.98 1720.96 L1342.7 1720.96 L1342.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1342.7,1720.96 1342.7,1720.96 1342.98,1720.96 1342.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1342.98 1720.96 L1342.98 1720.96 L1343.27 1720.96 L1343.27 1720.96 L1342.98 1720.96 L1342.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1342.98,1720.96 1342.98,1720.96 1343.27,1720.96 1342.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1343.27 1720.76 L1343.27 1720.96 L1343.55 1720.96 L1343.55 1720.76 L1343.27 1720.76 L1343.27 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1343.27,1720.76 1343.27,1720.96 1343.55,1720.96 1343.55,1720.76 1343.27,1720.76 "/>
<path clip-path="url(#clip322)" d="M1343.55 1720.76 L1343.55 1720.96 L1343.83 1720.96 L1343.83 1720.76 L1343.55 1720.76 L1343.55 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1343.55,1720.76 1343.55,1720.96 1343.83,1720.96 1343.83,1720.76 1343.55,1720.76 "/>
<path clip-path="url(#clip322)" d="M1343.83 1720.96 L1343.83 1720.96 L1344.11 1720.96 L1344.11 1720.96 L1343.83 1720.96 L1343.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1343.83,1720.96 1343.83,1720.96 1344.11,1720.96 1343.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1344.11 1720.96 L1344.11 1720.96 L1344.39 1720.96 L1344.39 1720.96 L1344.11 1720.96 L1344.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1344.11,1720.96 1344.11,1720.96 1344.39,1720.96 1344.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1344.39 1720.96 L1344.39 1720.96 L1344.67 1720.96 L1344.67 1720.96 L1344.39 1720.96 L1344.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1344.39,1720.96 1344.39,1720.96 1344.67,1720.96 1344.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1344.67 1720.96 L1344.67 1720.96 L1344.96 1720.96 L1344.96 1720.96 L1344.67 1720.96 L1344.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1344.67,1720.96 1344.67,1720.96 1344.96,1720.96 1344.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1344.96 1720.96 L1344.96 1720.96 L1345.24 1720.96 L1345.24 1720.96 L1344.96 1720.96 L1344.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1344.96,1720.96 1344.96,1720.96 1345.24,1720.96 1344.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1345.24 1720.96 L1345.24 1720.96 L1345.52 1720.96 L1345.52 1720.96 L1345.24 1720.96 L1345.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1345.24,1720.96 1345.24,1720.96 1345.52,1720.96 1345.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1345.52 1720.96 L1345.52 1720.96 L1345.8 1720.96 L1345.8 1720.96 L1345.52 1720.96 L1345.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1345.52,1720.96 1345.52,1720.96 1345.8,1720.96 1345.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1345.8 1720.76 L1345.8 1720.96 L1346.08 1720.96 L1346.08 1720.76 L1345.8 1720.76 L1345.8 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1345.8,1720.76 1345.8,1720.96 1346.08,1720.96 1346.08,1720.76 1345.8,1720.76 "/>
<path clip-path="url(#clip322)" d="M1346.08 1720.96 L1346.08 1720.96 L1346.36 1720.96 L1346.36 1720.96 L1346.08 1720.96 L1346.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1346.08,1720.96 1346.08,1720.96 1346.36,1720.96 1346.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1346.36 1720.96 L1346.36 1720.96 L1346.65 1720.96 L1346.65 1720.96 L1346.36 1720.96 L1346.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1346.36,1720.96 1346.36,1720.96 1346.65,1720.96 1346.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1346.65 1720.76 L1346.65 1720.96 L1346.93 1720.96 L1346.93 1720.76 L1346.65 1720.76 L1346.65 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1346.65,1720.76 1346.65,1720.96 1346.93,1720.96 1346.93,1720.76 1346.65,1720.76 "/>
<path clip-path="url(#clip322)" d="M1346.93 1720.96 L1346.93 1720.96 L1347.21 1720.96 L1347.21 1720.96 L1346.93 1720.96 L1346.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1346.93,1720.96 1346.93,1720.96 1347.21,1720.96 1346.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1347.21 1720.96 L1347.21 1720.96 L1347.49 1720.96 L1347.49 1720.96 L1347.21 1720.96 L1347.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1347.21,1720.96 1347.21,1720.96 1347.49,1720.96 1347.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1347.49 1720.96 L1347.49 1720.96 L1347.77 1720.96 L1347.77 1720.96 L1347.49 1720.96 L1347.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1347.49,1720.96 1347.49,1720.96 1347.77,1720.96 1347.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1347.77 1720.76 L1347.77 1720.96 L1348.05 1720.96 L1348.05 1720.76 L1347.77 1720.76 L1347.77 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1347.77,1720.76 1347.77,1720.96 1348.05,1720.96 1348.05,1720.76 1347.77,1720.76 "/>
<path clip-path="url(#clip322)" d="M1348.05 1720.96 L1348.05 1720.96 L1348.34 1720.96 L1348.34 1720.96 L1348.05 1720.96 L1348.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1348.05,1720.96 1348.05,1720.96 1348.34,1720.96 1348.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1348.34 1720.96 L1348.34 1720.96 L1348.62 1720.96 L1348.62 1720.96 L1348.34 1720.96 L1348.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1348.34,1720.96 1348.34,1720.96 1348.62,1720.96 1348.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1348.62 1720.96 L1348.62 1720.96 L1348.9 1720.96 L1348.9 1720.96 L1348.62 1720.96 L1348.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1348.62,1720.96 1348.62,1720.96 1348.9,1720.96 1348.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1348.9 1720.96 L1348.9 1720.96 L1349.18 1720.96 L1349.18 1720.96 L1348.9 1720.96 L1348.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1348.9,1720.96 1348.9,1720.96 1349.18,1720.96 1348.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1349.18 1720.96 L1349.18 1720.96 L1349.46 1720.96 L1349.46 1720.96 L1349.18 1720.96 L1349.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1349.18,1720.96 1349.18,1720.96 1349.46,1720.96 1349.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1349.46 1720.96 L1349.46 1720.96 L1349.75 1720.96 L1349.75 1720.96 L1349.46 1720.96 L1349.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1349.46,1720.96 1349.46,1720.96 1349.75,1720.96 1349.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1349.75 1720.96 L1349.75 1720.96 L1350.03 1720.96 L1350.03 1720.96 L1349.75 1720.96 L1349.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1349.75,1720.96 1349.75,1720.96 1350.03,1720.96 1349.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1350.03 1720.96 L1350.03 1720.96 L1350.31 1720.96 L1350.31 1720.96 L1350.03 1720.96 L1350.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1350.03,1720.96 1350.03,1720.96 1350.31,1720.96 1350.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1350.31 1720.96 L1350.31 1720.96 L1350.59 1720.96 L1350.59 1720.96 L1350.31 1720.96 L1350.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1350.31,1720.96 1350.31,1720.96 1350.59,1720.96 1350.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1350.59 1720.96 L1350.59 1720.96 L1350.87 1720.96 L1350.87 1720.96 L1350.59 1720.96 L1350.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1350.59,1720.96 1350.59,1720.96 1350.87,1720.96 1350.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1350.87 1720.96 L1350.87 1720.96 L1351.15 1720.96 L1351.15 1720.96 L1350.87 1720.96 L1350.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1350.87,1720.96 1350.87,1720.96 1351.15,1720.96 1350.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1351.15 1720.96 L1351.15 1720.96 L1351.44 1720.96 L1351.44 1720.96 L1351.15 1720.96 L1351.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1351.15,1720.96 1351.15,1720.96 1351.44,1720.96 1351.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1351.44 1720.96 L1351.44 1720.96 L1351.72 1720.96 L1351.72 1720.96 L1351.44 1720.96 L1351.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1351.44,1720.96 1351.44,1720.96 1351.72,1720.96 1351.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1351.72 1720.96 L1351.72 1720.96 L1352 1720.96 L1352 1720.96 L1351.72 1720.96 L1351.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1351.72,1720.96 1351.72,1720.96 1352,1720.96 1351.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1352 1720.96 L1352 1720.96 L1352.28 1720.96 L1352.28 1720.96 L1352 1720.96 L1352 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1352,1720.96 1352,1720.96 1352.28,1720.96 1352,1720.96 "/>
<path clip-path="url(#clip322)" d="M1352.28 1720.96 L1352.28 1720.96 L1352.56 1720.96 L1352.56 1720.96 L1352.28 1720.96 L1352.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1352.28,1720.96 1352.28,1720.96 1352.56,1720.96 1352.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1352.56 1720.96 L1352.56 1720.96 L1352.84 1720.96 L1352.84 1720.96 L1352.56 1720.96 L1352.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1352.56,1720.96 1352.56,1720.96 1352.84,1720.96 1352.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1352.84 1720.96 L1352.84 1720.96 L1353.13 1720.96 L1353.13 1720.96 L1352.84 1720.96 L1352.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1352.84,1720.96 1352.84,1720.96 1353.13,1720.96 1352.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1353.13 1720.96 L1353.13 1720.96 L1353.41 1720.96 L1353.41 1720.96 L1353.13 1720.96 L1353.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1353.13,1720.96 1353.13,1720.96 1353.41,1720.96 1353.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1353.41 1720.96 L1353.41 1720.96 L1353.69 1720.96 L1353.69 1720.96 L1353.41 1720.96 L1353.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1353.41,1720.96 1353.41,1720.96 1353.69,1720.96 1353.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1353.69 1720.96 L1353.69 1720.96 L1353.97 1720.96 L1353.97 1720.96 L1353.69 1720.96 L1353.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1353.69,1720.96 1353.69,1720.96 1353.97,1720.96 1353.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1353.97 1720.96 L1353.97 1720.96 L1354.25 1720.96 L1354.25 1720.96 L1353.97 1720.96 L1353.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1353.97,1720.96 1353.97,1720.96 1354.25,1720.96 1353.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1354.25 1720.96 L1354.25 1720.96 L1354.53 1720.96 L1354.53 1720.96 L1354.25 1720.96 L1354.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1354.25,1720.96 1354.25,1720.96 1354.53,1720.96 1354.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1354.53 1720.96 L1354.53 1720.96 L1354.82 1720.96 L1354.82 1720.96 L1354.53 1720.96 L1354.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1354.53,1720.96 1354.53,1720.96 1354.82,1720.96 1354.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1354.82 1720.96 L1354.82 1720.96 L1355.1 1720.96 L1355.1 1720.96 L1354.82 1720.96 L1354.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1354.82,1720.96 1354.82,1720.96 1355.1,1720.96 1354.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1355.1 1720.96 L1355.1 1720.96 L1355.38 1720.96 L1355.38 1720.96 L1355.1 1720.96 L1355.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1355.1,1720.96 1355.1,1720.96 1355.38,1720.96 1355.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1355.38 1720.96 L1355.38 1720.96 L1355.66 1720.96 L1355.66 1720.96 L1355.38 1720.96 L1355.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1355.38,1720.96 1355.38,1720.96 1355.66,1720.96 1355.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1355.66 1720.96 L1355.66 1720.96 L1355.94 1720.96 L1355.94 1720.96 L1355.66 1720.96 L1355.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1355.66,1720.96 1355.66,1720.96 1355.94,1720.96 1355.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1355.94 1720.96 L1355.94 1720.96 L1356.22 1720.96 L1356.22 1720.96 L1355.94 1720.96 L1355.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1355.94,1720.96 1355.94,1720.96 1356.22,1720.96 1355.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1356.22 1720.96 L1356.22 1720.96 L1356.51 1720.96 L1356.51 1720.96 L1356.22 1720.96 L1356.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1356.22,1720.96 1356.22,1720.96 1356.51,1720.96 1356.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1356.51 1720.96 L1356.51 1720.96 L1356.79 1720.96 L1356.79 1720.96 L1356.51 1720.96 L1356.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1356.51,1720.96 1356.51,1720.96 1356.79,1720.96 1356.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1356.79 1720.96 L1356.79 1720.96 L1357.07 1720.96 L1357.07 1720.96 L1356.79 1720.96 L1356.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1356.79,1720.96 1356.79,1720.96 1357.07,1720.96 1356.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1357.07 1720.96 L1357.07 1720.96 L1357.35 1720.96 L1357.35 1720.96 L1357.07 1720.96 L1357.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1357.07,1720.96 1357.07,1720.96 1357.35,1720.96 1357.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1357.35 1720.96 L1357.35 1720.96 L1357.63 1720.96 L1357.63 1720.96 L1357.35 1720.96 L1357.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1357.35,1720.96 1357.35,1720.96 1357.63,1720.96 1357.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1357.63 1720.96 L1357.63 1720.96 L1357.92 1720.96 L1357.92 1720.96 L1357.63 1720.96 L1357.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1357.63,1720.96 1357.63,1720.96 1357.92,1720.96 1357.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1357.92 1720.96 L1357.92 1720.96 L1358.2 1720.96 L1358.2 1720.96 L1357.92 1720.96 L1357.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1357.92,1720.96 1357.92,1720.96 1358.2,1720.96 1357.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1358.2 1720.96 L1358.2 1720.96 L1358.48 1720.96 L1358.48 1720.96 L1358.2 1720.96 L1358.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1358.2,1720.96 1358.2,1720.96 1358.48,1720.96 1358.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1358.48 1720.96 L1358.48 1720.96 L1358.76 1720.96 L1358.76 1720.96 L1358.48 1720.96 L1358.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1358.48,1720.96 1358.48,1720.96 1358.76,1720.96 1358.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1358.76 1720.96 L1358.76 1720.96 L1359.04 1720.96 L1359.04 1720.96 L1358.76 1720.96 L1358.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1358.76,1720.96 1358.76,1720.96 1359.04,1720.96 1358.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1359.04 1720.96 L1359.04 1720.96 L1359.32 1720.96 L1359.32 1720.96 L1359.04 1720.96 L1359.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1359.04,1720.96 1359.04,1720.96 1359.32,1720.96 1359.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1359.32 1720.96 L1359.32 1720.96 L1359.61 1720.96 L1359.61 1720.96 L1359.32 1720.96 L1359.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1359.32,1720.96 1359.32,1720.96 1359.61,1720.96 1359.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1359.61 1720.96 L1359.61 1720.96 L1359.89 1720.96 L1359.89 1720.96 L1359.61 1720.96 L1359.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1359.61,1720.96 1359.61,1720.96 1359.89,1720.96 1359.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1359.89 1720.96 L1359.89 1720.96 L1360.17 1720.96 L1360.17 1720.96 L1359.89 1720.96 L1359.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1359.89,1720.96 1359.89,1720.96 1360.17,1720.96 1359.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1360.17 1720.76 L1360.17 1720.96 L1360.45 1720.96 L1360.45 1720.76 L1360.17 1720.76 L1360.17 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1360.17,1720.76 1360.17,1720.96 1360.45,1720.96 1360.45,1720.76 1360.17,1720.76 "/>
<path clip-path="url(#clip322)" d="M1360.45 1720.96 L1360.45 1720.96 L1360.73 1720.96 L1360.73 1720.96 L1360.45 1720.96 L1360.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1360.45,1720.96 1360.45,1720.96 1360.73,1720.96 1360.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1360.73 1720.96 L1360.73 1720.96 L1361.01 1720.96 L1361.01 1720.96 L1360.73 1720.96 L1360.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1360.73,1720.96 1360.73,1720.96 1361.01,1720.96 1360.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1361.01 1720.96 L1361.01 1720.96 L1361.3 1720.96 L1361.3 1720.96 L1361.01 1720.96 L1361.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1361.01,1720.96 1361.01,1720.96 1361.3,1720.96 1361.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1361.3 1720.96 L1361.3 1720.96 L1361.58 1720.96 L1361.58 1720.96 L1361.3 1720.96 L1361.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1361.3,1720.96 1361.3,1720.96 1361.58,1720.96 1361.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1361.58 1720.96 L1361.58 1720.96 L1361.86 1720.96 L1361.86 1720.96 L1361.58 1720.96 L1361.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1361.58,1720.96 1361.58,1720.96 1361.86,1720.96 1361.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1361.86 1720.96 L1361.86 1720.96 L1362.14 1720.96 L1362.14 1720.96 L1361.86 1720.96 L1361.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1361.86,1720.96 1361.86,1720.96 1362.14,1720.96 1361.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1362.14 1720.96 L1362.14 1720.96 L1362.42 1720.96 L1362.42 1720.96 L1362.14 1720.96 L1362.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1362.14,1720.96 1362.14,1720.96 1362.42,1720.96 1362.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1362.42 1720.96 L1362.42 1720.96 L1362.7 1720.96 L1362.7 1720.96 L1362.42 1720.96 L1362.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1362.42,1720.96 1362.42,1720.96 1362.7,1720.96 1362.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1362.7 1720.96 L1362.7 1720.96 L1362.99 1720.96 L1362.99 1720.96 L1362.7 1720.96 L1362.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1362.7,1720.96 1362.7,1720.96 1362.99,1720.96 1362.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1362.99 1720.96 L1362.99 1720.96 L1363.27 1720.96 L1363.27 1720.96 L1362.99 1720.96 L1362.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1362.99,1720.96 1362.99,1720.96 1363.27,1720.96 1362.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1363.27 1720.96 L1363.27 1720.96 L1363.55 1720.96 L1363.55 1720.96 L1363.27 1720.96 L1363.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1363.27,1720.96 1363.27,1720.96 1363.55,1720.96 1363.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1363.55 1720.96 L1363.55 1720.96 L1363.83 1720.96 L1363.83 1720.96 L1363.55 1720.96 L1363.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1363.55,1720.96 1363.55,1720.96 1363.83,1720.96 1363.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1363.83 1720.96 L1363.83 1720.96 L1364.11 1720.96 L1364.11 1720.96 L1363.83 1720.96 L1363.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1363.83,1720.96 1363.83,1720.96 1364.11,1720.96 1363.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1364.11 1720.96 L1364.11 1720.96 L1364.39 1720.96 L1364.39 1720.96 L1364.11 1720.96 L1364.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1364.11,1720.96 1364.11,1720.96 1364.39,1720.96 1364.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1364.39 1720.96 L1364.39 1720.96 L1364.68 1720.96 L1364.68 1720.96 L1364.39 1720.96 L1364.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1364.39,1720.96 1364.39,1720.96 1364.68,1720.96 1364.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1364.68 1720.96 L1364.68 1720.96 L1364.96 1720.96 L1364.96 1720.96 L1364.68 1720.96 L1364.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1364.68,1720.96 1364.68,1720.96 1364.96,1720.96 1364.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1364.96 1720.96 L1364.96 1720.96 L1365.24 1720.96 L1365.24 1720.96 L1364.96 1720.96 L1364.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1364.96,1720.96 1364.96,1720.96 1365.24,1720.96 1364.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1365.24 1720.96 L1365.24 1720.96 L1365.52 1720.96 L1365.52 1720.96 L1365.24 1720.96 L1365.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1365.24,1720.96 1365.24,1720.96 1365.52,1720.96 1365.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1365.52 1720.76 L1365.52 1720.96 L1365.8 1720.96 L1365.8 1720.76 L1365.52 1720.76 L1365.52 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1365.52,1720.76 1365.52,1720.96 1365.8,1720.96 1365.8,1720.76 1365.52,1720.76 "/>
<path clip-path="url(#clip322)" d="M1365.8 1720.96 L1365.8 1720.96 L1366.09 1720.96 L1366.09 1720.96 L1365.8 1720.96 L1365.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1365.8,1720.96 1365.8,1720.96 1366.09,1720.96 1365.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1366.09 1720.96 L1366.09 1720.96 L1366.37 1720.96 L1366.37 1720.96 L1366.09 1720.96 L1366.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1366.09,1720.96 1366.09,1720.96 1366.37,1720.96 1366.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1366.37 1720.96 L1366.37 1720.96 L1366.65 1720.96 L1366.65 1720.96 L1366.37 1720.96 L1366.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1366.37,1720.96 1366.37,1720.96 1366.65,1720.96 1366.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1366.65 1720.96 L1366.65 1720.96 L1366.93 1720.96 L1366.93 1720.96 L1366.65 1720.96 L1366.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1366.65,1720.96 1366.65,1720.96 1366.93,1720.96 1366.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1366.93 1720.96 L1366.93 1720.96 L1367.21 1720.96 L1367.21 1720.96 L1366.93 1720.96 L1366.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1366.93,1720.96 1366.93,1720.96 1367.21,1720.96 1366.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1367.21 1720.96 L1367.21 1720.96 L1367.49 1720.96 L1367.49 1720.96 L1367.21 1720.96 L1367.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1367.21,1720.96 1367.21,1720.96 1367.49,1720.96 1367.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1367.49 1720.96 L1367.49 1720.96 L1367.78 1720.96 L1367.78 1720.96 L1367.49 1720.96 L1367.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1367.49,1720.96 1367.49,1720.96 1367.78,1720.96 1367.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1367.78 1720.96 L1367.78 1720.96 L1368.06 1720.96 L1368.06 1720.96 L1367.78 1720.96 L1367.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1367.78,1720.96 1367.78,1720.96 1368.06,1720.96 1367.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1368.06 1720.76 L1368.06 1720.96 L1368.34 1720.96 L1368.34 1720.76 L1368.06 1720.76 L1368.06 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1368.06,1720.76 1368.06,1720.96 1368.34,1720.96 1368.34,1720.76 1368.06,1720.76 "/>
<path clip-path="url(#clip322)" d="M1368.34 1720.96 L1368.34 1720.96 L1368.62 1720.96 L1368.62 1720.96 L1368.34 1720.96 L1368.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1368.34,1720.96 1368.34,1720.96 1368.62,1720.96 1368.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1368.62 1720.96 L1368.62 1720.96 L1368.9 1720.96 L1368.9 1720.96 L1368.62 1720.96 L1368.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1368.62,1720.96 1368.62,1720.96 1368.9,1720.96 1368.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1368.9 1720.96 L1368.9 1720.96 L1369.18 1720.96 L1369.18 1720.96 L1368.9 1720.96 L1368.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1368.9,1720.96 1368.9,1720.96 1369.18,1720.96 1368.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1369.18 1720.96 L1369.18 1720.96 L1369.47 1720.96 L1369.47 1720.96 L1369.18 1720.96 L1369.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1369.18,1720.96 1369.18,1720.96 1369.47,1720.96 1369.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1369.47 1720.96 L1369.47 1720.96 L1369.75 1720.96 L1369.75 1720.96 L1369.47 1720.96 L1369.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1369.47,1720.96 1369.47,1720.96 1369.75,1720.96 1369.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1369.75 1720.96 L1369.75 1720.96 L1370.03 1720.96 L1370.03 1720.96 L1369.75 1720.96 L1369.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1369.75,1720.96 1369.75,1720.96 1370.03,1720.96 1369.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1370.03 1720.96 L1370.03 1720.96 L1370.31 1720.96 L1370.31 1720.96 L1370.03 1720.96 L1370.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1370.03,1720.96 1370.03,1720.96 1370.31,1720.96 1370.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1370.31 1720.96 L1370.31 1720.96 L1370.59 1720.96 L1370.59 1720.96 L1370.31 1720.96 L1370.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1370.31,1720.96 1370.31,1720.96 1370.59,1720.96 1370.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1370.59 1720.96 L1370.59 1720.96 L1370.87 1720.96 L1370.87 1720.96 L1370.59 1720.96 L1370.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1370.59,1720.96 1370.59,1720.96 1370.87,1720.96 1370.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1370.87 1720.96 L1370.87 1720.96 L1371.16 1720.96 L1371.16 1720.96 L1370.87 1720.96 L1370.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1370.87,1720.96 1370.87,1720.96 1371.16,1720.96 1370.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1371.16 1720.96 L1371.16 1720.96 L1371.44 1720.96 L1371.44 1720.96 L1371.16 1720.96 L1371.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1371.16,1720.96 1371.16,1720.96 1371.44,1720.96 1371.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1371.44 1720.76 L1371.44 1720.96 L1371.72 1720.96 L1371.72 1720.76 L1371.44 1720.76 L1371.44 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1371.44,1720.76 1371.44,1720.96 1371.72,1720.96 1371.72,1720.76 1371.44,1720.76 "/>
<path clip-path="url(#clip322)" d="M1371.72 1720.96 L1371.72 1720.96 L1372 1720.96 L1372 1720.96 L1371.72 1720.96 L1371.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1371.72,1720.96 1371.72,1720.96 1372,1720.96 1371.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1372 1720.96 L1372 1720.96 L1372.28 1720.96 L1372.28 1720.96 L1372 1720.96 L1372 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1372,1720.96 1372,1720.96 1372.28,1720.96 1372,1720.96 "/>
<path clip-path="url(#clip322)" d="M1372.28 1720.96 L1372.28 1720.96 L1372.56 1720.96 L1372.56 1720.96 L1372.28 1720.96 L1372.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1372.28,1720.96 1372.28,1720.96 1372.56,1720.96 1372.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1372.56 1720.96 L1372.56 1720.96 L1372.85 1720.96 L1372.85 1720.96 L1372.56 1720.96 L1372.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1372.56,1720.96 1372.56,1720.96 1372.85,1720.96 1372.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1372.85 1720.96 L1372.85 1720.96 L1373.13 1720.96 L1373.13 1720.96 L1372.85 1720.96 L1372.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1372.85,1720.96 1372.85,1720.96 1373.13,1720.96 1372.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1373.13 1720.96 L1373.13 1720.96 L1373.41 1720.96 L1373.41 1720.96 L1373.13 1720.96 L1373.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1373.13,1720.96 1373.13,1720.96 1373.41,1720.96 1373.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1373.41 1720.96 L1373.41 1720.96 L1373.69 1720.96 L1373.69 1720.96 L1373.41 1720.96 L1373.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1373.41,1720.96 1373.41,1720.96 1373.69,1720.96 1373.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1373.69 1720.96 L1373.69 1720.96 L1373.97 1720.96 L1373.97 1720.96 L1373.69 1720.96 L1373.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1373.69,1720.96 1373.69,1720.96 1373.97,1720.96 1373.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1373.97 1720.96 L1373.97 1720.96 L1374.26 1720.96 L1374.26 1720.96 L1373.97 1720.96 L1373.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1373.97,1720.96 1373.97,1720.96 1374.26,1720.96 1373.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1374.26 1720.96 L1374.26 1720.96 L1374.54 1720.96 L1374.54 1720.96 L1374.26 1720.96 L1374.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1374.26,1720.96 1374.26,1720.96 1374.54,1720.96 1374.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1374.54 1720.96 L1374.54 1720.96 L1374.82 1720.96 L1374.82 1720.96 L1374.54 1720.96 L1374.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1374.54,1720.96 1374.54,1720.96 1374.82,1720.96 1374.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1374.82 1720.96 L1374.82 1720.96 L1375.1 1720.96 L1375.1 1720.96 L1374.82 1720.96 L1374.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1374.82,1720.96 1374.82,1720.96 1375.1,1720.96 1374.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1375.1 1720.96 L1375.1 1720.96 L1375.38 1720.96 L1375.38 1720.96 L1375.1 1720.96 L1375.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1375.1,1720.96 1375.1,1720.96 1375.38,1720.96 1375.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1375.38 1720.96 L1375.38 1720.96 L1375.66 1720.96 L1375.66 1720.96 L1375.38 1720.96 L1375.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1375.38,1720.96 1375.38,1720.96 1375.66,1720.96 1375.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1375.66 1720.96 L1375.66 1720.96 L1375.95 1720.96 L1375.95 1720.96 L1375.66 1720.96 L1375.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1375.66,1720.96 1375.66,1720.96 1375.95,1720.96 1375.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1375.95 1720.96 L1375.95 1720.96 L1376.23 1720.96 L1376.23 1720.96 L1375.95 1720.96 L1375.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1375.95,1720.96 1375.95,1720.96 1376.23,1720.96 1375.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1376.23 1720.96 L1376.23 1720.96 L1376.51 1720.96 L1376.51 1720.96 L1376.23 1720.96 L1376.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1376.23,1720.96 1376.23,1720.96 1376.51,1720.96 1376.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1376.51 1720.96 L1376.51 1720.96 L1376.79 1720.96 L1376.79 1720.96 L1376.51 1720.96 L1376.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1376.51,1720.96 1376.51,1720.96 1376.79,1720.96 1376.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1376.79 1720.96 L1376.79 1720.96 L1377.07 1720.96 L1377.07 1720.96 L1376.79 1720.96 L1376.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1376.79,1720.96 1376.79,1720.96 1377.07,1720.96 1376.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1377.07 1720.96 L1377.07 1720.96 L1377.35 1720.96 L1377.35 1720.96 L1377.07 1720.96 L1377.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1377.07,1720.96 1377.07,1720.96 1377.35,1720.96 1377.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1377.35 1720.96 L1377.35 1720.96 L1377.64 1720.96 L1377.64 1720.96 L1377.35 1720.96 L1377.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1377.35,1720.96 1377.35,1720.96 1377.64,1720.96 1377.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1377.64 1720.96 L1377.64 1720.96 L1377.92 1720.96 L1377.92 1720.96 L1377.64 1720.96 L1377.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1377.64,1720.96 1377.64,1720.96 1377.92,1720.96 1377.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1377.92 1720.96 L1377.92 1720.96 L1378.2 1720.96 L1378.2 1720.96 L1377.92 1720.96 L1377.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1377.92,1720.96 1377.92,1720.96 1378.2,1720.96 1377.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1378.2 1720.96 L1378.2 1720.96 L1378.48 1720.96 L1378.48 1720.96 L1378.2 1720.96 L1378.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1378.2,1720.96 1378.2,1720.96 1378.48,1720.96 1378.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1378.48 1720.96 L1378.48 1720.96 L1378.76 1720.96 L1378.76 1720.96 L1378.48 1720.96 L1378.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1378.48,1720.96 1378.48,1720.96 1378.76,1720.96 1378.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1378.76 1720.96 L1378.76 1720.96 L1379.04 1720.96 L1379.04 1720.96 L1378.76 1720.96 L1378.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1378.76,1720.96 1378.76,1720.96 1379.04,1720.96 1378.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1379.04 1720.96 L1379.04 1720.96 L1379.33 1720.96 L1379.33 1720.96 L1379.04 1720.96 L1379.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1379.04,1720.96 1379.04,1720.96 1379.33,1720.96 1379.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1379.33 1720.96 L1379.33 1720.96 L1379.61 1720.96 L1379.61 1720.96 L1379.33 1720.96 L1379.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1379.33,1720.96 1379.33,1720.96 1379.61,1720.96 1379.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1379.61 1720.96 L1379.61 1720.96 L1379.89 1720.96 L1379.89 1720.96 L1379.61 1720.96 L1379.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1379.61,1720.96 1379.61,1720.96 1379.89,1720.96 1379.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1379.89 1720.96 L1379.89 1720.96 L1380.17 1720.96 L1380.17 1720.96 L1379.89 1720.96 L1379.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1379.89,1720.96 1379.89,1720.96 1380.17,1720.96 1379.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1380.17 1720.96 L1380.17 1720.96 L1380.45 1720.96 L1380.45 1720.96 L1380.17 1720.96 L1380.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1380.17,1720.96 1380.17,1720.96 1380.45,1720.96 1380.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1380.45 1720.76 L1380.45 1720.96 L1380.73 1720.96 L1380.73 1720.76 L1380.45 1720.76 L1380.45 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1380.45,1720.76 1380.45,1720.96 1380.73,1720.96 1380.73,1720.76 1380.45,1720.76 "/>
<path clip-path="url(#clip322)" d="M1380.73 1720.96 L1380.73 1720.96 L1381.02 1720.96 L1381.02 1720.96 L1380.73 1720.96 L1380.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1380.73,1720.96 1380.73,1720.96 1381.02,1720.96 1380.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1381.02 1720.96 L1381.02 1720.96 L1381.3 1720.96 L1381.3 1720.96 L1381.02 1720.96 L1381.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1381.02,1720.96 1381.02,1720.96 1381.3,1720.96 1381.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1381.3 1720.76 L1381.3 1720.96 L1381.58 1720.96 L1381.58 1720.76 L1381.3 1720.76 L1381.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1381.3,1720.76 1381.3,1720.96 1381.58,1720.96 1381.58,1720.76 1381.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1381.58 1720.96 L1381.58 1720.96 L1381.86 1720.96 L1381.86 1720.96 L1381.58 1720.96 L1381.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1381.58,1720.96 1381.58,1720.96 1381.86,1720.96 1381.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1381.86 1720.96 L1381.86 1720.96 L1382.14 1720.96 L1382.14 1720.96 L1381.86 1720.96 L1381.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1381.86,1720.96 1381.86,1720.96 1382.14,1720.96 1381.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1382.14 1720.76 L1382.14 1720.96 L1382.43 1720.96 L1382.43 1720.76 L1382.14 1720.76 L1382.14 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1382.14,1720.76 1382.14,1720.96 1382.43,1720.96 1382.43,1720.76 1382.14,1720.76 "/>
<path clip-path="url(#clip322)" d="M1382.43 1720.96 L1382.43 1720.96 L1382.71 1720.96 L1382.71 1720.96 L1382.43 1720.96 L1382.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1382.43,1720.96 1382.43,1720.96 1382.71,1720.96 1382.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1382.71 1720.96 L1382.71 1720.96 L1382.99 1720.96 L1382.99 1720.96 L1382.71 1720.96 L1382.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1382.71,1720.96 1382.71,1720.96 1382.99,1720.96 1382.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1382.99 1720.96 L1382.99 1720.96 L1383.27 1720.96 L1383.27 1720.96 L1382.99 1720.96 L1382.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1382.99,1720.96 1382.99,1720.96 1383.27,1720.96 1382.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1383.27 1720.96 L1383.27 1720.96 L1383.55 1720.96 L1383.55 1720.96 L1383.27 1720.96 L1383.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1383.27,1720.96 1383.27,1720.96 1383.55,1720.96 1383.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1383.55 1720.96 L1383.55 1720.96 L1383.83 1720.96 L1383.83 1720.96 L1383.55 1720.96 L1383.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1383.55,1720.96 1383.55,1720.96 1383.83,1720.96 1383.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1383.83 1720.96 L1383.83 1720.96 L1384.12 1720.96 L1384.12 1720.96 L1383.83 1720.96 L1383.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1383.83,1720.96 1383.83,1720.96 1384.12,1720.96 1383.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1384.12 1720.96 L1384.12 1720.96 L1384.4 1720.96 L1384.4 1720.96 L1384.12 1720.96 L1384.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1384.12,1720.96 1384.12,1720.96 1384.4,1720.96 1384.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1384.4 1720.96 L1384.4 1720.96 L1384.68 1720.96 L1384.68 1720.96 L1384.4 1720.96 L1384.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1384.4,1720.96 1384.4,1720.96 1384.68,1720.96 1384.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1384.68 1720.96 L1384.68 1720.96 L1384.96 1720.96 L1384.96 1720.96 L1384.68 1720.96 L1384.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1384.68,1720.96 1384.68,1720.96 1384.96,1720.96 1384.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1384.96 1720.96 L1384.96 1720.96 L1385.24 1720.96 L1385.24 1720.96 L1384.96 1720.96 L1384.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1384.96,1720.96 1384.96,1720.96 1385.24,1720.96 1384.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1385.24 1720.96 L1385.24 1720.96 L1385.52 1720.96 L1385.52 1720.96 L1385.24 1720.96 L1385.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1385.24,1720.96 1385.24,1720.96 1385.52,1720.96 1385.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1385.52 1720.96 L1385.52 1720.96 L1385.81 1720.96 L1385.81 1720.96 L1385.52 1720.96 L1385.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1385.52,1720.96 1385.52,1720.96 1385.81,1720.96 1385.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1385.81 1720.96 L1385.81 1720.96 L1386.09 1720.96 L1386.09 1720.96 L1385.81 1720.96 L1385.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1385.81,1720.96 1385.81,1720.96 1386.09,1720.96 1385.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1386.09 1720.96 L1386.09 1720.96 L1386.37 1720.96 L1386.37 1720.96 L1386.09 1720.96 L1386.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1386.09,1720.96 1386.09,1720.96 1386.37,1720.96 1386.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1386.37 1720.96 L1386.37 1720.96 L1386.65 1720.96 L1386.65 1720.96 L1386.37 1720.96 L1386.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1386.37,1720.96 1386.37,1720.96 1386.65,1720.96 1386.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1386.65 1720.96 L1386.65 1720.96 L1386.93 1720.96 L1386.93 1720.96 L1386.65 1720.96 L1386.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1386.65,1720.96 1386.65,1720.96 1386.93,1720.96 1386.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1386.93 1720.96 L1386.93 1720.96 L1387.21 1720.96 L1387.21 1720.96 L1386.93 1720.96 L1386.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1386.93,1720.96 1386.93,1720.96 1387.21,1720.96 1386.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1387.21 1720.96 L1387.21 1720.96 L1387.5 1720.96 L1387.5 1720.96 L1387.21 1720.96 L1387.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1387.21,1720.96 1387.21,1720.96 1387.5,1720.96 1387.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1387.5 1720.96 L1387.5 1720.96 L1387.78 1720.96 L1387.78 1720.96 L1387.5 1720.96 L1387.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1387.5,1720.96 1387.5,1720.96 1387.78,1720.96 1387.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1387.78 1720.76 L1387.78 1720.96 L1388.06 1720.96 L1388.06 1720.76 L1387.78 1720.76 L1387.78 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1387.78,1720.76 1387.78,1720.96 1388.06,1720.96 1388.06,1720.76 1387.78,1720.76 "/>
<path clip-path="url(#clip322)" d="M1388.06 1720.96 L1388.06 1720.96 L1388.34 1720.96 L1388.34 1720.96 L1388.06 1720.96 L1388.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1388.06,1720.96 1388.06,1720.96 1388.34,1720.96 1388.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1388.34 1720.96 L1388.34 1720.96 L1388.62 1720.96 L1388.62 1720.96 L1388.34 1720.96 L1388.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1388.34,1720.96 1388.34,1720.96 1388.62,1720.96 1388.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1388.62 1720.96 L1388.62 1720.96 L1388.91 1720.96 L1388.91 1720.96 L1388.62 1720.96 L1388.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1388.62,1720.96 1388.62,1720.96 1388.91,1720.96 1388.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1388.91 1720.96 L1388.91 1720.96 L1389.19 1720.96 L1389.19 1720.96 L1388.91 1720.96 L1388.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1388.91,1720.96 1388.91,1720.96 1389.19,1720.96 1388.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1389.19 1720.96 L1389.19 1720.96 L1389.47 1720.96 L1389.47 1720.96 L1389.19 1720.96 L1389.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1389.19,1720.96 1389.19,1720.96 1389.47,1720.96 1389.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1389.47 1720.96 L1389.47 1720.96 L1389.75 1720.96 L1389.75 1720.96 L1389.47 1720.96 L1389.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1389.47,1720.96 1389.47,1720.96 1389.75,1720.96 1389.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1389.75 1720.96 L1389.75 1720.96 L1390.03 1720.96 L1390.03 1720.96 L1389.75 1720.96 L1389.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1389.75,1720.96 1389.75,1720.96 1390.03,1720.96 1389.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1390.03 1720.96 L1390.03 1720.96 L1390.31 1720.96 L1390.31 1720.96 L1390.03 1720.96 L1390.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1390.03,1720.96 1390.03,1720.96 1390.31,1720.96 1390.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1390.31 1720.96 L1390.31 1720.96 L1390.6 1720.96 L1390.6 1720.96 L1390.31 1720.96 L1390.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1390.31,1720.96 1390.31,1720.96 1390.6,1720.96 1390.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1390.6 1720.96 L1390.6 1720.96 L1390.88 1720.96 L1390.88 1720.96 L1390.6 1720.96 L1390.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1390.6,1720.96 1390.6,1720.96 1390.88,1720.96 1390.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1390.88 1720.96 L1390.88 1720.96 L1391.16 1720.96 L1391.16 1720.96 L1390.88 1720.96 L1390.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1390.88,1720.96 1390.88,1720.96 1391.16,1720.96 1390.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1391.16 1720.96 L1391.16 1720.96 L1391.44 1720.96 L1391.44 1720.96 L1391.16 1720.96 L1391.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1391.16,1720.96 1391.16,1720.96 1391.44,1720.96 1391.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1391.44 1720.96 L1391.44 1720.96 L1391.72 1720.96 L1391.72 1720.96 L1391.44 1720.96 L1391.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1391.44,1720.96 1391.44,1720.96 1391.72,1720.96 1391.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1391.72 1720.96 L1391.72 1720.96 L1392 1720.96 L1392 1720.96 L1391.72 1720.96 L1391.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1391.72,1720.96 1391.72,1720.96 1392,1720.96 1391.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1392 1720.96 L1392 1720.96 L1392.29 1720.96 L1392.29 1720.96 L1392 1720.96 L1392 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1392,1720.96 1392,1720.96 1392.29,1720.96 1392,1720.96 "/>
<path clip-path="url(#clip322)" d="M1392.29 1720.96 L1392.29 1720.96 L1392.57 1720.96 L1392.57 1720.96 L1392.29 1720.96 L1392.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1392.29,1720.96 1392.29,1720.96 1392.57,1720.96 1392.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1392.57 1720.96 L1392.57 1720.96 L1392.85 1720.96 L1392.85 1720.96 L1392.57 1720.96 L1392.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1392.57,1720.96 1392.57,1720.96 1392.85,1720.96 1392.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1392.85 1720.96 L1392.85 1720.96 L1393.13 1720.96 L1393.13 1720.96 L1392.85 1720.96 L1392.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1392.85,1720.96 1392.85,1720.96 1393.13,1720.96 1392.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1393.13 1720.96 L1393.13 1720.96 L1393.41 1720.96 L1393.41 1720.96 L1393.13 1720.96 L1393.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1393.13,1720.96 1393.13,1720.96 1393.41,1720.96 1393.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1393.41 1720.96 L1393.41 1720.96 L1393.69 1720.96 L1393.69 1720.96 L1393.41 1720.96 L1393.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1393.41,1720.96 1393.41,1720.96 1393.69,1720.96 1393.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1393.69 1720.96 L1393.69 1720.96 L1393.98 1720.96 L1393.98 1720.96 L1393.69 1720.96 L1393.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1393.69,1720.96 1393.69,1720.96 1393.98,1720.96 1393.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1393.98 1720.96 L1393.98 1720.96 L1394.26 1720.96 L1394.26 1720.96 L1393.98 1720.96 L1393.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1393.98,1720.96 1393.98,1720.96 1394.26,1720.96 1393.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1394.26 1720.96 L1394.26 1720.96 L1394.54 1720.96 L1394.54 1720.96 L1394.26 1720.96 L1394.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1394.26,1720.96 1394.26,1720.96 1394.54,1720.96 1394.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1394.54 1720.96 L1394.54 1720.96 L1394.82 1720.96 L1394.82 1720.96 L1394.54 1720.96 L1394.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1394.54,1720.96 1394.54,1720.96 1394.82,1720.96 1394.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1394.82 1720.96 L1394.82 1720.96 L1395.1 1720.96 L1395.1 1720.96 L1394.82 1720.96 L1394.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1394.82,1720.96 1394.82,1720.96 1395.1,1720.96 1394.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1395.1 1720.96 L1395.1 1720.96 L1395.38 1720.96 L1395.38 1720.96 L1395.1 1720.96 L1395.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1395.1,1720.96 1395.1,1720.96 1395.38,1720.96 1395.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1395.38 1720.96 L1395.38 1720.96 L1395.67 1720.96 L1395.67 1720.96 L1395.38 1720.96 L1395.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1395.38,1720.96 1395.38,1720.96 1395.67,1720.96 1395.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1395.67 1720.96 L1395.67 1720.96 L1395.95 1720.96 L1395.95 1720.96 L1395.67 1720.96 L1395.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1395.67,1720.96 1395.67,1720.96 1395.95,1720.96 1395.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1395.95 1720.96 L1395.95 1720.96 L1396.23 1720.96 L1396.23 1720.96 L1395.95 1720.96 L1395.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1395.95,1720.96 1395.95,1720.96 1396.23,1720.96 1395.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1396.23 1720.96 L1396.23 1720.96 L1396.51 1720.96 L1396.51 1720.96 L1396.23 1720.96 L1396.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1396.23,1720.96 1396.23,1720.96 1396.51,1720.96 1396.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1396.51 1720.96 L1396.51 1720.96 L1396.79 1720.96 L1396.79 1720.96 L1396.51 1720.96 L1396.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1396.51,1720.96 1396.51,1720.96 1396.79,1720.96 1396.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1396.79 1720.96 L1396.79 1720.96 L1397.08 1720.96 L1397.08 1720.96 L1396.79 1720.96 L1396.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1396.79,1720.96 1396.79,1720.96 1397.08,1720.96 1396.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1397.08 1720.96 L1397.08 1720.96 L1397.36 1720.96 L1397.36 1720.96 L1397.08 1720.96 L1397.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1397.08,1720.96 1397.08,1720.96 1397.36,1720.96 1397.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1397.36 1720.96 L1397.36 1720.96 L1397.64 1720.96 L1397.64 1720.96 L1397.36 1720.96 L1397.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1397.36,1720.96 1397.36,1720.96 1397.64,1720.96 1397.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1397.64 1720.96 L1397.64 1720.96 L1397.92 1720.96 L1397.92 1720.96 L1397.64 1720.96 L1397.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1397.64,1720.96 1397.64,1720.96 1397.92,1720.96 1397.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1397.92 1720.96 L1397.92 1720.96 L1398.2 1720.96 L1398.2 1720.96 L1397.92 1720.96 L1397.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1397.92,1720.96 1397.92,1720.96 1398.2,1720.96 1397.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1398.2 1720.76 L1398.2 1720.96 L1398.48 1720.96 L1398.48 1720.76 L1398.2 1720.76 L1398.2 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1398.2,1720.76 1398.2,1720.96 1398.48,1720.96 1398.48,1720.76 1398.2,1720.76 "/>
<path clip-path="url(#clip322)" d="M1398.48 1720.96 L1398.48 1720.96 L1398.77 1720.96 L1398.77 1720.96 L1398.48 1720.96 L1398.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1398.48,1720.96 1398.48,1720.96 1398.77,1720.96 1398.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1398.77 1720.96 L1398.77 1720.96 L1399.05 1720.96 L1399.05 1720.96 L1398.77 1720.96 L1398.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1398.77,1720.96 1398.77,1720.96 1399.05,1720.96 1398.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1399.05 1720.96 L1399.05 1720.96 L1399.33 1720.96 L1399.33 1720.96 L1399.05 1720.96 L1399.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1399.05,1720.96 1399.05,1720.96 1399.33,1720.96 1399.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1399.33 1720.96 L1399.33 1720.96 L1399.61 1720.96 L1399.61 1720.96 L1399.33 1720.96 L1399.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1399.33,1720.96 1399.33,1720.96 1399.61,1720.96 1399.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1399.61 1720.96 L1399.61 1720.96 L1399.89 1720.96 L1399.89 1720.96 L1399.61 1720.96 L1399.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1399.61,1720.96 1399.61,1720.96 1399.89,1720.96 1399.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1399.89 1720.96 L1399.89 1720.96 L1400.17 1720.96 L1400.17 1720.96 L1399.89 1720.96 L1399.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1399.89,1720.96 1399.89,1720.96 1400.17,1720.96 1399.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1400.17 1720.96 L1400.17 1720.96 L1400.46 1720.96 L1400.46 1720.96 L1400.17 1720.96 L1400.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1400.17,1720.96 1400.17,1720.96 1400.46,1720.96 1400.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1400.46 1720.96 L1400.46 1720.96 L1400.74 1720.96 L1400.74 1720.96 L1400.46 1720.96 L1400.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1400.46,1720.96 1400.46,1720.96 1400.74,1720.96 1400.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1400.74 1720.96 L1400.74 1720.96 L1401.02 1720.96 L1401.02 1720.96 L1400.74 1720.96 L1400.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1400.74,1720.96 1400.74,1720.96 1401.02,1720.96 1400.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1401.02 1720.96 L1401.02 1720.96 L1401.3 1720.96 L1401.3 1720.96 L1401.02 1720.96 L1401.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1401.02,1720.96 1401.02,1720.96 1401.3,1720.96 1401.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1401.3 1720.96 L1401.3 1720.96 L1401.58 1720.96 L1401.58 1720.96 L1401.3 1720.96 L1401.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1401.3,1720.96 1401.3,1720.96 1401.58,1720.96 1401.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1401.58 1720.96 L1401.58 1720.96 L1401.86 1720.96 L1401.86 1720.96 L1401.58 1720.96 L1401.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1401.58,1720.96 1401.58,1720.96 1401.86,1720.96 1401.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1401.86 1720.96 L1401.86 1720.96 L1402.15 1720.96 L1402.15 1720.96 L1401.86 1720.96 L1401.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1401.86,1720.96 1401.86,1720.96 1402.15,1720.96 1401.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1402.15 1720.96 L1402.15 1720.96 L1402.43 1720.96 L1402.43 1720.96 L1402.15 1720.96 L1402.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1402.15,1720.96 1402.15,1720.96 1402.43,1720.96 1402.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1402.43 1720.96 L1402.43 1720.96 L1402.71 1720.96 L1402.71 1720.96 L1402.43 1720.96 L1402.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1402.43,1720.96 1402.43,1720.96 1402.71,1720.96 1402.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1402.71 1720.76 L1402.71 1720.96 L1402.99 1720.96 L1402.99 1720.76 L1402.71 1720.76 L1402.71 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1402.71,1720.76 1402.71,1720.96 1402.99,1720.96 1402.99,1720.76 1402.71,1720.76 "/>
<path clip-path="url(#clip322)" d="M1402.99 1720.76 L1402.99 1720.96 L1403.27 1720.96 L1403.27 1720.76 L1402.99 1720.76 L1402.99 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1402.99,1720.76 1402.99,1720.96 1403.27,1720.96 1403.27,1720.76 1402.99,1720.76 "/>
<path clip-path="url(#clip322)" d="M1403.27 1720.96 L1403.27 1720.96 L1403.55 1720.96 L1403.55 1720.96 L1403.27 1720.96 L1403.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1403.27,1720.96 1403.27,1720.96 1403.55,1720.96 1403.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1403.55 1720.96 L1403.55 1720.96 L1403.84 1720.96 L1403.84 1720.96 L1403.55 1720.96 L1403.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1403.55,1720.96 1403.55,1720.96 1403.84,1720.96 1403.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1403.84 1720.96 L1403.84 1720.96 L1404.12 1720.96 L1404.12 1720.96 L1403.84 1720.96 L1403.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1403.84,1720.96 1403.84,1720.96 1404.12,1720.96 1403.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1404.12 1720.96 L1404.12 1720.96 L1404.4 1720.96 L1404.4 1720.96 L1404.12 1720.96 L1404.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1404.12,1720.96 1404.12,1720.96 1404.4,1720.96 1404.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1404.4 1720.96 L1404.4 1720.96 L1404.68 1720.96 L1404.68 1720.96 L1404.4 1720.96 L1404.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1404.4,1720.96 1404.4,1720.96 1404.68,1720.96 1404.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1404.68 1720.96 L1404.68 1720.96 L1404.96 1720.96 L1404.96 1720.96 L1404.68 1720.96 L1404.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1404.68,1720.96 1404.68,1720.96 1404.96,1720.96 1404.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1404.96 1720.96 L1404.96 1720.96 L1405.25 1720.96 L1405.25 1720.96 L1404.96 1720.96 L1404.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1404.96,1720.96 1404.96,1720.96 1405.25,1720.96 1404.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1405.25 1720.96 L1405.25 1720.96 L1405.53 1720.96 L1405.53 1720.96 L1405.25 1720.96 L1405.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1405.25,1720.96 1405.25,1720.96 1405.53,1720.96 1405.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1405.53 1720.96 L1405.53 1720.96 L1405.81 1720.96 L1405.81 1720.96 L1405.53 1720.96 L1405.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1405.53,1720.96 1405.53,1720.96 1405.81,1720.96 1405.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1405.81 1720.96 L1405.81 1720.96 L1406.09 1720.96 L1406.09 1720.96 L1405.81 1720.96 L1405.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1405.81,1720.96 1405.81,1720.96 1406.09,1720.96 1405.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1406.09 1720.96 L1406.09 1720.96 L1406.37 1720.96 L1406.37 1720.96 L1406.09 1720.96 L1406.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1406.09,1720.96 1406.09,1720.96 1406.37,1720.96 1406.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1406.37 1720.96 L1406.37 1720.96 L1406.65 1720.96 L1406.65 1720.96 L1406.37 1720.96 L1406.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1406.37,1720.96 1406.37,1720.96 1406.65,1720.96 1406.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1406.65 1720.96 L1406.65 1720.96 L1406.94 1720.96 L1406.94 1720.96 L1406.65 1720.96 L1406.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1406.65,1720.96 1406.65,1720.96 1406.94,1720.96 1406.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1406.94 1720.96 L1406.94 1720.96 L1407.22 1720.96 L1407.22 1720.96 L1406.94 1720.96 L1406.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1406.94,1720.96 1406.94,1720.96 1407.22,1720.96 1406.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1407.22 1720.96 L1407.22 1720.96 L1407.5 1720.96 L1407.5 1720.96 L1407.22 1720.96 L1407.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1407.22,1720.96 1407.22,1720.96 1407.5,1720.96 1407.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1407.5 1720.96 L1407.5 1720.96 L1407.78 1720.96 L1407.78 1720.96 L1407.5 1720.96 L1407.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1407.5,1720.96 1407.5,1720.96 1407.78,1720.96 1407.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1407.78 1720.96 L1407.78 1720.96 L1408.06 1720.96 L1408.06 1720.96 L1407.78 1720.96 L1407.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1407.78,1720.96 1407.78,1720.96 1408.06,1720.96 1407.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1408.06 1720.96 L1408.06 1720.96 L1408.34 1720.96 L1408.34 1720.96 L1408.06 1720.96 L1408.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1408.06,1720.96 1408.06,1720.96 1408.34,1720.96 1408.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1408.34 1720.96 L1408.34 1720.96 L1408.63 1720.96 L1408.63 1720.96 L1408.34 1720.96 L1408.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1408.34,1720.96 1408.34,1720.96 1408.63,1720.96 1408.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1408.63 1720.96 L1408.63 1720.96 L1408.91 1720.96 L1408.91 1720.96 L1408.63 1720.96 L1408.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1408.63,1720.96 1408.63,1720.96 1408.91,1720.96 1408.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1408.91 1720.96 L1408.91 1720.96 L1409.19 1720.96 L1409.19 1720.96 L1408.91 1720.96 L1408.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1408.91,1720.96 1408.91,1720.96 1409.19,1720.96 1408.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1409.19 1720.96 L1409.19 1720.96 L1409.47 1720.96 L1409.47 1720.96 L1409.19 1720.96 L1409.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1409.19,1720.96 1409.19,1720.96 1409.47,1720.96 1409.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1409.47 1720.96 L1409.47 1720.96 L1409.75 1720.96 L1409.75 1720.96 L1409.47 1720.96 L1409.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1409.47,1720.96 1409.47,1720.96 1409.75,1720.96 1409.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1409.75 1720.96 L1409.75 1720.96 L1410.03 1720.96 L1410.03 1720.96 L1409.75 1720.96 L1409.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1409.75,1720.96 1409.75,1720.96 1410.03,1720.96 1409.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1410.03 1720.96 L1410.03 1720.96 L1410.32 1720.96 L1410.32 1720.96 L1410.03 1720.96 L1410.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1410.03,1720.96 1410.03,1720.96 1410.32,1720.96 1410.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1410.32 1720.96 L1410.32 1720.96 L1410.6 1720.96 L1410.6 1720.96 L1410.32 1720.96 L1410.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1410.32,1720.96 1410.32,1720.96 1410.6,1720.96 1410.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1410.6 1720.96 L1410.6 1720.96 L1410.88 1720.96 L1410.88 1720.96 L1410.6 1720.96 L1410.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1410.6,1720.96 1410.6,1720.96 1410.88,1720.96 1410.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1410.88 1720.96 L1410.88 1720.96 L1411.16 1720.96 L1411.16 1720.96 L1410.88 1720.96 L1410.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1410.88,1720.96 1410.88,1720.96 1411.16,1720.96 1410.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1411.16 1720.96 L1411.16 1720.96 L1411.44 1720.96 L1411.44 1720.96 L1411.16 1720.96 L1411.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1411.16,1720.96 1411.16,1720.96 1411.44,1720.96 1411.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1411.44 1720.96 L1411.44 1720.96 L1411.72 1720.96 L1411.72 1720.96 L1411.44 1720.96 L1411.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1411.44,1720.96 1411.44,1720.96 1411.72,1720.96 1411.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1411.72 1720.96 L1411.72 1720.96 L1412.01 1720.96 L1412.01 1720.96 L1411.72 1720.96 L1411.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1411.72,1720.96 1411.72,1720.96 1412.01,1720.96 1411.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1412.01 1720.96 L1412.01 1720.96 L1412.29 1720.96 L1412.29 1720.96 L1412.01 1720.96 L1412.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1412.01,1720.96 1412.01,1720.96 1412.29,1720.96 1412.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1412.29 1720.76 L1412.29 1720.96 L1412.57 1720.96 L1412.57 1720.76 L1412.29 1720.76 L1412.29 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1412.29,1720.76 1412.29,1720.96 1412.57,1720.96 1412.57,1720.76 1412.29,1720.76 "/>
<path clip-path="url(#clip322)" d="M1412.57 1720.96 L1412.57 1720.96 L1412.85 1720.96 L1412.85 1720.96 L1412.57 1720.96 L1412.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1412.57,1720.96 1412.57,1720.96 1412.85,1720.96 1412.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1412.85 1720.96 L1412.85 1720.96 L1413.13 1720.96 L1413.13 1720.96 L1412.85 1720.96 L1412.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1412.85,1720.96 1412.85,1720.96 1413.13,1720.96 1412.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1413.13 1720.96 L1413.13 1720.96 L1413.42 1720.96 L1413.42 1720.96 L1413.13 1720.96 L1413.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1413.13,1720.96 1413.13,1720.96 1413.42,1720.96 1413.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1413.42 1720.96 L1413.42 1720.96 L1413.7 1720.96 L1413.7 1720.96 L1413.42 1720.96 L1413.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1413.42,1720.96 1413.42,1720.96 1413.7,1720.96 1413.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1413.7 1720.96 L1413.7 1720.96 L1413.98 1720.96 L1413.98 1720.96 L1413.7 1720.96 L1413.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1413.7,1720.96 1413.7,1720.96 1413.98,1720.96 1413.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1413.98 1720.96 L1413.98 1720.96 L1414.26 1720.96 L1414.26 1720.96 L1413.98 1720.96 L1413.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1413.98,1720.96 1413.98,1720.96 1414.26,1720.96 1413.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1414.26 1720.96 L1414.26 1720.96 L1414.54 1720.96 L1414.54 1720.96 L1414.26 1720.96 L1414.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1414.26,1720.96 1414.26,1720.96 1414.54,1720.96 1414.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1414.54 1720.96 L1414.54 1720.96 L1414.82 1720.96 L1414.82 1720.96 L1414.54 1720.96 L1414.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1414.54,1720.96 1414.54,1720.96 1414.82,1720.96 1414.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1414.82 1720.96 L1414.82 1720.96 L1415.11 1720.96 L1415.11 1720.96 L1414.82 1720.96 L1414.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1414.82,1720.96 1414.82,1720.96 1415.11,1720.96 1414.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1415.11 1720.96 L1415.11 1720.96 L1415.39 1720.96 L1415.39 1720.96 L1415.11 1720.96 L1415.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1415.11,1720.96 1415.11,1720.96 1415.39,1720.96 1415.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1415.39 1720.96 L1415.39 1720.96 L1415.67 1720.96 L1415.67 1720.96 L1415.39 1720.96 L1415.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1415.39,1720.96 1415.39,1720.96 1415.67,1720.96 1415.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1415.67 1720.96 L1415.67 1720.96 L1415.95 1720.96 L1415.95 1720.96 L1415.67 1720.96 L1415.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1415.67,1720.96 1415.67,1720.96 1415.95,1720.96 1415.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1415.95 1720.96 L1415.95 1720.96 L1416.23 1720.96 L1416.23 1720.96 L1415.95 1720.96 L1415.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1415.95,1720.96 1415.95,1720.96 1416.23,1720.96 1415.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1416.23 1720.96 L1416.23 1720.96 L1416.51 1720.96 L1416.51 1720.96 L1416.23 1720.96 L1416.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1416.23,1720.96 1416.23,1720.96 1416.51,1720.96 1416.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1416.51 1720.96 L1416.51 1720.96 L1416.8 1720.96 L1416.8 1720.96 L1416.51 1720.96 L1416.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1416.51,1720.96 1416.51,1720.96 1416.8,1720.96 1416.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1416.8 1720.96 L1416.8 1720.96 L1417.08 1720.96 L1417.08 1720.96 L1416.8 1720.96 L1416.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1416.8,1720.96 1416.8,1720.96 1417.08,1720.96 1416.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1417.08 1720.96 L1417.08 1720.96 L1417.36 1720.96 L1417.36 1720.96 L1417.08 1720.96 L1417.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1417.08,1720.96 1417.08,1720.96 1417.36,1720.96 1417.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1417.36 1720.96 L1417.36 1720.96 L1417.64 1720.96 L1417.64 1720.96 L1417.36 1720.96 L1417.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1417.36,1720.96 1417.36,1720.96 1417.64,1720.96 1417.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1417.64 1720.96 L1417.64 1720.96 L1417.92 1720.96 L1417.92 1720.96 L1417.64 1720.96 L1417.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1417.64,1720.96 1417.64,1720.96 1417.92,1720.96 1417.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1417.92 1720.96 L1417.92 1720.96 L1418.2 1720.96 L1418.2 1720.96 L1417.92 1720.96 L1417.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1417.92,1720.96 1417.92,1720.96 1418.2,1720.96 1417.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1418.2 1720.96 L1418.2 1720.96 L1418.49 1720.96 L1418.49 1720.96 L1418.2 1720.96 L1418.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1418.2,1720.96 1418.2,1720.96 1418.49,1720.96 1418.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1418.49 1720.96 L1418.49 1720.96 L1418.77 1720.96 L1418.77 1720.96 L1418.49 1720.96 L1418.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1418.49,1720.96 1418.49,1720.96 1418.77,1720.96 1418.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1418.77 1720.96 L1418.77 1720.96 L1419.05 1720.96 L1419.05 1720.96 L1418.77 1720.96 L1418.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1418.77,1720.96 1418.77,1720.96 1419.05,1720.96 1418.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1419.05 1720.96 L1419.05 1720.96 L1419.33 1720.96 L1419.33 1720.96 L1419.05 1720.96 L1419.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1419.05,1720.96 1419.05,1720.96 1419.33,1720.96 1419.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1419.33 1720.96 L1419.33 1720.96 L1419.61 1720.96 L1419.61 1720.96 L1419.33 1720.96 L1419.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1419.33,1720.96 1419.33,1720.96 1419.61,1720.96 1419.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1419.61 1720.96 L1419.61 1720.96 L1419.89 1720.96 L1419.89 1720.96 L1419.61 1720.96 L1419.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1419.61,1720.96 1419.61,1720.96 1419.89,1720.96 1419.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1419.89 1720.96 L1419.89 1720.96 L1420.18 1720.96 L1420.18 1720.96 L1419.89 1720.96 L1419.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1419.89,1720.96 1419.89,1720.96 1420.18,1720.96 1419.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1420.18 1720.96 L1420.18 1720.96 L1420.46 1720.96 L1420.46 1720.96 L1420.18 1720.96 L1420.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1420.18,1720.96 1420.18,1720.96 1420.46,1720.96 1420.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1420.46 1720.76 L1420.46 1720.96 L1420.74 1720.96 L1420.74 1720.76 L1420.46 1720.76 L1420.46 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1420.46,1720.76 1420.46,1720.96 1420.74,1720.96 1420.74,1720.76 1420.46,1720.76 "/>
<path clip-path="url(#clip322)" d="M1420.74 1720.96 L1420.74 1720.96 L1421.02 1720.96 L1421.02 1720.96 L1420.74 1720.96 L1420.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1420.74,1720.96 1420.74,1720.96 1421.02,1720.96 1420.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1421.02 1720.96 L1421.02 1720.96 L1421.3 1720.96 L1421.3 1720.96 L1421.02 1720.96 L1421.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1421.02,1720.96 1421.02,1720.96 1421.3,1720.96 1421.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1421.3 1720.96 L1421.3 1720.96 L1421.59 1720.96 L1421.59 1720.96 L1421.3 1720.96 L1421.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1421.3,1720.96 1421.3,1720.96 1421.59,1720.96 1421.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1421.59 1720.96 L1421.59 1720.96 L1421.87 1720.96 L1421.87 1720.96 L1421.59 1720.96 L1421.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1421.59,1720.96 1421.59,1720.96 1421.87,1720.96 1421.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1421.87 1720.96 L1421.87 1720.96 L1422.15 1720.96 L1422.15 1720.96 L1421.87 1720.96 L1421.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1421.87,1720.96 1421.87,1720.96 1422.15,1720.96 1421.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1422.15 1720.76 L1422.15 1720.96 L1422.43 1720.96 L1422.43 1720.76 L1422.15 1720.76 L1422.15 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1422.15,1720.76 1422.15,1720.96 1422.43,1720.96 1422.43,1720.76 1422.15,1720.76 "/>
<path clip-path="url(#clip322)" d="M1422.43 1720.96 L1422.43 1720.96 L1422.71 1720.96 L1422.71 1720.96 L1422.43 1720.96 L1422.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1422.43,1720.96 1422.43,1720.96 1422.71,1720.96 1422.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1422.71 1720.96 L1422.71 1720.96 L1422.99 1720.96 L1422.99 1720.96 L1422.71 1720.96 L1422.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1422.71,1720.96 1422.71,1720.96 1422.99,1720.96 1422.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1422.99 1720.96 L1422.99 1720.96 L1423.28 1720.96 L1423.28 1720.96 L1422.99 1720.96 L1422.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1422.99,1720.96 1422.99,1720.96 1423.28,1720.96 1422.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1423.28 1720.76 L1423.28 1720.96 L1423.56 1720.96 L1423.56 1720.76 L1423.28 1720.76 L1423.28 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1423.28,1720.76 1423.28,1720.96 1423.56,1720.96 1423.56,1720.76 1423.28,1720.76 "/>
<path clip-path="url(#clip322)" d="M1423.56 1720.96 L1423.56 1720.96 L1423.84 1720.96 L1423.84 1720.96 L1423.56 1720.96 L1423.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1423.56,1720.96 1423.56,1720.96 1423.84,1720.96 1423.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1423.84 1720.96 L1423.84 1720.96 L1424.12 1720.96 L1424.12 1720.96 L1423.84 1720.96 L1423.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1423.84,1720.96 1423.84,1720.96 1424.12,1720.96 1423.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1424.12 1720.96 L1424.12 1720.96 L1424.4 1720.96 L1424.4 1720.96 L1424.12 1720.96 L1424.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1424.12,1720.96 1424.12,1720.96 1424.4,1720.96 1424.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1424.4 1720.96 L1424.4 1720.96 L1424.68 1720.96 L1424.68 1720.96 L1424.4 1720.96 L1424.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1424.4,1720.96 1424.4,1720.96 1424.68,1720.96 1424.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1424.68 1720.96 L1424.68 1720.96 L1424.97 1720.96 L1424.97 1720.96 L1424.68 1720.96 L1424.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1424.68,1720.96 1424.68,1720.96 1424.97,1720.96 1424.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1424.97 1720.96 L1424.97 1720.96 L1425.25 1720.96 L1425.25 1720.96 L1424.97 1720.96 L1424.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1424.97,1720.96 1424.97,1720.96 1425.25,1720.96 1424.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1425.25 1720.96 L1425.25 1720.96 L1425.53 1720.96 L1425.53 1720.96 L1425.25 1720.96 L1425.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1425.25,1720.96 1425.25,1720.96 1425.53,1720.96 1425.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1425.53 1720.96 L1425.53 1720.96 L1425.81 1720.96 L1425.81 1720.96 L1425.53 1720.96 L1425.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1425.53,1720.96 1425.53,1720.96 1425.81,1720.96 1425.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1425.81 1720.96 L1425.81 1720.96 L1426.09 1720.96 L1426.09 1720.96 L1425.81 1720.96 L1425.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1425.81,1720.96 1425.81,1720.96 1426.09,1720.96 1425.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1426.09 1720.96 L1426.09 1720.96 L1426.37 1720.96 L1426.37 1720.96 L1426.09 1720.96 L1426.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1426.09,1720.96 1426.09,1720.96 1426.37,1720.96 1426.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1426.37 1720.96 L1426.37 1720.96 L1426.66 1720.96 L1426.66 1720.96 L1426.37 1720.96 L1426.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1426.37,1720.96 1426.37,1720.96 1426.66,1720.96 1426.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1426.66 1720.96 L1426.66 1720.96 L1426.94 1720.96 L1426.94 1720.96 L1426.66 1720.96 L1426.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1426.66,1720.96 1426.66,1720.96 1426.94,1720.96 1426.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1426.94 1720.96 L1426.94 1720.96 L1427.22 1720.96 L1427.22 1720.96 L1426.94 1720.96 L1426.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1426.94,1720.96 1426.94,1720.96 1427.22,1720.96 1426.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1427.22 1720.96 L1427.22 1720.96 L1427.5 1720.96 L1427.5 1720.96 L1427.22 1720.96 L1427.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1427.22,1720.96 1427.22,1720.96 1427.5,1720.96 1427.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1427.5 1720.96 L1427.5 1720.96 L1427.78 1720.96 L1427.78 1720.96 L1427.5 1720.96 L1427.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1427.5,1720.96 1427.5,1720.96 1427.78,1720.96 1427.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1427.78 1720.96 L1427.78 1720.96 L1428.06 1720.96 L1428.06 1720.96 L1427.78 1720.96 L1427.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1427.78,1720.96 1427.78,1720.96 1428.06,1720.96 1427.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1428.06 1720.96 L1428.06 1720.96 L1428.35 1720.96 L1428.35 1720.96 L1428.06 1720.96 L1428.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1428.06,1720.96 1428.06,1720.96 1428.35,1720.96 1428.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1428.35 1720.96 L1428.35 1720.96 L1428.63 1720.96 L1428.63 1720.96 L1428.35 1720.96 L1428.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1428.35,1720.96 1428.35,1720.96 1428.63,1720.96 1428.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1428.63 1720.96 L1428.63 1720.96 L1428.91 1720.96 L1428.91 1720.96 L1428.63 1720.96 L1428.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1428.63,1720.96 1428.63,1720.96 1428.91,1720.96 1428.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1428.91 1720.96 L1428.91 1720.96 L1429.19 1720.96 L1429.19 1720.96 L1428.91 1720.96 L1428.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1428.91,1720.96 1428.91,1720.96 1429.19,1720.96 1428.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1429.19 1720.96 L1429.19 1720.96 L1429.47 1720.96 L1429.47 1720.96 L1429.19 1720.96 L1429.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1429.19,1720.96 1429.19,1720.96 1429.47,1720.96 1429.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1429.47 1720.96 L1429.47 1720.96 L1429.76 1720.96 L1429.76 1720.96 L1429.47 1720.96 L1429.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1429.47,1720.96 1429.47,1720.96 1429.76,1720.96 1429.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1429.76 1720.96 L1429.76 1720.96 L1430.04 1720.96 L1430.04 1720.96 L1429.76 1720.96 L1429.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1429.76,1720.96 1429.76,1720.96 1430.04,1720.96 1429.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1430.04 1720.96 L1430.04 1720.96 L1430.32 1720.96 L1430.32 1720.96 L1430.04 1720.96 L1430.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1430.04,1720.96 1430.04,1720.96 1430.32,1720.96 1430.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1430.32 1720.96 L1430.32 1720.96 L1430.6 1720.96 L1430.6 1720.96 L1430.32 1720.96 L1430.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1430.32,1720.96 1430.32,1720.96 1430.6,1720.96 1430.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1430.6 1720.96 L1430.6 1720.96 L1430.88 1720.96 L1430.88 1720.96 L1430.6 1720.96 L1430.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1430.6,1720.96 1430.6,1720.96 1430.88,1720.96 1430.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1430.88 1720.96 L1430.88 1720.96 L1431.16 1720.96 L1431.16 1720.96 L1430.88 1720.96 L1430.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1430.88,1720.96 1430.88,1720.96 1431.16,1720.96 1430.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1431.16 1720.96 L1431.16 1720.96 L1431.45 1720.96 L1431.45 1720.96 L1431.16 1720.96 L1431.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1431.16,1720.96 1431.16,1720.96 1431.45,1720.96 1431.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1431.45 1720.96 L1431.45 1720.96 L1431.73 1720.96 L1431.73 1720.96 L1431.45 1720.96 L1431.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1431.45,1720.96 1431.45,1720.96 1431.73,1720.96 1431.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1431.73 1720.96 L1431.73 1720.96 L1432.01 1720.96 L1432.01 1720.96 L1431.73 1720.96 L1431.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1431.73,1720.96 1431.73,1720.96 1432.01,1720.96 1431.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1432.01 1720.96 L1432.01 1720.96 L1432.29 1720.96 L1432.29 1720.96 L1432.01 1720.96 L1432.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1432.01,1720.96 1432.01,1720.96 1432.29,1720.96 1432.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1432.29 1720.96 L1432.29 1720.96 L1432.57 1720.96 L1432.57 1720.96 L1432.29 1720.96 L1432.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1432.29,1720.96 1432.29,1720.96 1432.57,1720.96 1432.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1432.57 1720.96 L1432.57 1720.96 L1432.85 1720.96 L1432.85 1720.96 L1432.57 1720.96 L1432.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1432.57,1720.96 1432.57,1720.96 1432.85,1720.96 1432.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1432.85 1720.96 L1432.85 1720.96 L1433.14 1720.96 L1433.14 1720.96 L1432.85 1720.96 L1432.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1432.85,1720.96 1432.85,1720.96 1433.14,1720.96 1432.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1433.14 1720.96 L1433.14 1720.96 L1433.42 1720.96 L1433.42 1720.96 L1433.14 1720.96 L1433.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1433.14,1720.96 1433.14,1720.96 1433.42,1720.96 1433.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1433.42 1720.96 L1433.42 1720.96 L1433.7 1720.96 L1433.7 1720.96 L1433.42 1720.96 L1433.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1433.42,1720.96 1433.42,1720.96 1433.7,1720.96 1433.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1433.7 1720.96 L1433.7 1720.96 L1433.98 1720.96 L1433.98 1720.96 L1433.7 1720.96 L1433.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1433.7,1720.96 1433.7,1720.96 1433.98,1720.96 1433.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1433.98 1720.96 L1433.98 1720.96 L1434.26 1720.96 L1434.26 1720.96 L1433.98 1720.96 L1433.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1433.98,1720.96 1433.98,1720.96 1434.26,1720.96 1433.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1434.26 1720.96 L1434.26 1720.96 L1434.54 1720.96 L1434.54 1720.96 L1434.26 1720.96 L1434.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1434.26,1720.96 1434.26,1720.96 1434.54,1720.96 1434.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1434.54 1720.96 L1434.54 1720.96 L1434.83 1720.96 L1434.83 1720.96 L1434.54 1720.96 L1434.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1434.54,1720.96 1434.54,1720.96 1434.83,1720.96 1434.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1434.83 1720.96 L1434.83 1720.96 L1435.11 1720.96 L1435.11 1720.96 L1434.83 1720.96 L1434.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1434.83,1720.96 1434.83,1720.96 1435.11,1720.96 1434.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1435.11 1720.96 L1435.11 1720.96 L1435.39 1720.96 L1435.39 1720.96 L1435.11 1720.96 L1435.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1435.11,1720.96 1435.11,1720.96 1435.39,1720.96 1435.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1435.39 1720.96 L1435.39 1720.96 L1435.67 1720.96 L1435.67 1720.96 L1435.39 1720.96 L1435.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1435.39,1720.96 1435.39,1720.96 1435.67,1720.96 1435.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1435.67 1720.96 L1435.67 1720.96 L1435.95 1720.96 L1435.95 1720.96 L1435.67 1720.96 L1435.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1435.67,1720.96 1435.67,1720.96 1435.95,1720.96 1435.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1435.95 1720.96 L1435.95 1720.96 L1436.23 1720.96 L1436.23 1720.96 L1435.95 1720.96 L1435.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1435.95,1720.96 1435.95,1720.96 1436.23,1720.96 1435.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1436.23 1720.96 L1436.23 1720.96 L1436.52 1720.96 L1436.52 1720.96 L1436.23 1720.96 L1436.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1436.23,1720.96 1436.23,1720.96 1436.52,1720.96 1436.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1436.52 1720.96 L1436.52 1720.96 L1436.8 1720.96 L1436.8 1720.96 L1436.52 1720.96 L1436.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1436.52,1720.96 1436.52,1720.96 1436.8,1720.96 1436.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1436.8 1720.96 L1436.8 1720.96 L1437.08 1720.96 L1437.08 1720.96 L1436.8 1720.96 L1436.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1436.8,1720.96 1436.8,1720.96 1437.08,1720.96 1436.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1437.08 1720.96 L1437.08 1720.96 L1437.36 1720.96 L1437.36 1720.96 L1437.08 1720.96 L1437.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1437.08,1720.96 1437.08,1720.96 1437.36,1720.96 1437.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1437.36 1720.96 L1437.36 1720.96 L1437.64 1720.96 L1437.64 1720.96 L1437.36 1720.96 L1437.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1437.36,1720.96 1437.36,1720.96 1437.64,1720.96 1437.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1437.64 1720.96 L1437.64 1720.96 L1437.93 1720.96 L1437.93 1720.96 L1437.64 1720.96 L1437.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1437.64,1720.96 1437.64,1720.96 1437.93,1720.96 1437.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1437.93 1720.96 L1437.93 1720.96 L1438.21 1720.96 L1438.21 1720.96 L1437.93 1720.96 L1437.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1437.93,1720.96 1437.93,1720.96 1438.21,1720.96 1437.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1438.21 1720.96 L1438.21 1720.96 L1438.49 1720.96 L1438.49 1720.96 L1438.21 1720.96 L1438.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1438.21,1720.96 1438.21,1720.96 1438.49,1720.96 1438.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1438.49 1720.96 L1438.49 1720.96 L1438.77 1720.96 L1438.77 1720.96 L1438.49 1720.96 L1438.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1438.49,1720.96 1438.49,1720.96 1438.77,1720.96 1438.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1438.77 1720.96 L1438.77 1720.96 L1439.05 1720.96 L1439.05 1720.96 L1438.77 1720.96 L1438.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1438.77,1720.96 1438.77,1720.96 1439.05,1720.96 1438.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1439.05 1720.96 L1439.05 1720.96 L1439.33 1720.96 L1439.33 1720.96 L1439.05 1720.96 L1439.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1439.05,1720.96 1439.05,1720.96 1439.33,1720.96 1439.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1439.33 1720.96 L1439.33 1720.96 L1439.62 1720.96 L1439.62 1720.96 L1439.33 1720.96 L1439.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1439.33,1720.96 1439.33,1720.96 1439.62,1720.96 1439.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1439.62 1720.96 L1439.62 1720.96 L1439.9 1720.96 L1439.9 1720.96 L1439.62 1720.96 L1439.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1439.62,1720.96 1439.62,1720.96 1439.9,1720.96 1439.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1439.9 1720.96 L1439.9 1720.96 L1440.18 1720.96 L1440.18 1720.96 L1439.9 1720.96 L1439.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1439.9,1720.96 1439.9,1720.96 1440.18,1720.96 1439.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1440.18 1720.96 L1440.18 1720.96 L1440.46 1720.96 L1440.46 1720.96 L1440.18 1720.96 L1440.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1440.18,1720.96 1440.18,1720.96 1440.46,1720.96 1440.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1440.46 1720.96 L1440.46 1720.96 L1440.74 1720.96 L1440.74 1720.96 L1440.46 1720.96 L1440.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1440.46,1720.96 1440.46,1720.96 1440.74,1720.96 1440.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1440.74 1720.96 L1440.74 1720.96 L1441.02 1720.96 L1441.02 1720.96 L1440.74 1720.96 L1440.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1440.74,1720.96 1440.74,1720.96 1441.02,1720.96 1440.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1441.02 1720.96 L1441.02 1720.96 L1441.31 1720.96 L1441.31 1720.96 L1441.02 1720.96 L1441.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1441.02,1720.96 1441.02,1720.96 1441.31,1720.96 1441.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1441.31 1720.96 L1441.31 1720.96 L1441.59 1720.96 L1441.59 1720.96 L1441.31 1720.96 L1441.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1441.31,1720.96 1441.31,1720.96 1441.59,1720.96 1441.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1441.59 1720.96 L1441.59 1720.96 L1441.87 1720.96 L1441.87 1720.96 L1441.59 1720.96 L1441.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1441.59,1720.96 1441.59,1720.96 1441.87,1720.96 1441.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1441.87 1720.96 L1441.87 1720.96 L1442.15 1720.96 L1442.15 1720.96 L1441.87 1720.96 L1441.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1441.87,1720.96 1441.87,1720.96 1442.15,1720.96 1441.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1442.15 1720.96 L1442.15 1720.96 L1442.43 1720.96 L1442.43 1720.96 L1442.15 1720.96 L1442.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1442.15,1720.96 1442.15,1720.96 1442.43,1720.96 1442.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1442.43 1720.96 L1442.43 1720.96 L1442.71 1720.96 L1442.71 1720.96 L1442.43 1720.96 L1442.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1442.43,1720.96 1442.43,1720.96 1442.71,1720.96 1442.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1442.71 1720.96 L1442.71 1720.96 L1443 1720.96 L1443 1720.96 L1442.71 1720.96 L1442.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1442.71,1720.96 1442.71,1720.96 1443,1720.96 1442.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1443 1720.96 L1443 1720.96 L1443.28 1720.96 L1443.28 1720.96 L1443 1720.96 L1443 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1443,1720.96 1443,1720.96 1443.28,1720.96 1443,1720.96 "/>
<path clip-path="url(#clip322)" d="M1443.28 1720.96 L1443.28 1720.96 L1443.56 1720.96 L1443.56 1720.96 L1443.28 1720.96 L1443.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1443.28,1720.96 1443.28,1720.96 1443.56,1720.96 1443.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1443.56 1720.96 L1443.56 1720.96 L1443.84 1720.96 L1443.84 1720.96 L1443.56 1720.96 L1443.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1443.56,1720.96 1443.56,1720.96 1443.84,1720.96 1443.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1443.84 1720.96 L1443.84 1720.96 L1444.12 1720.96 L1444.12 1720.96 L1443.84 1720.96 L1443.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1443.84,1720.96 1443.84,1720.96 1444.12,1720.96 1443.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1444.12 1720.96 L1444.12 1720.96 L1444.4 1720.96 L1444.4 1720.96 L1444.12 1720.96 L1444.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1444.12,1720.96 1444.12,1720.96 1444.4,1720.96 1444.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1444.4 1720.96 L1444.4 1720.96 L1444.69 1720.96 L1444.69 1720.96 L1444.4 1720.96 L1444.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1444.4,1720.96 1444.4,1720.96 1444.69,1720.96 1444.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1444.69 1720.76 L1444.69 1720.96 L1444.97 1720.96 L1444.97 1720.76 L1444.69 1720.76 L1444.69 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1444.69,1720.76 1444.69,1720.96 1444.97,1720.96 1444.97,1720.76 1444.69,1720.76 "/>
<path clip-path="url(#clip322)" d="M1444.97 1720.96 L1444.97 1720.96 L1445.25 1720.96 L1445.25 1720.96 L1444.97 1720.96 L1444.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1444.97,1720.96 1444.97,1720.96 1445.25,1720.96 1444.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1445.25 1720.96 L1445.25 1720.96 L1445.53 1720.96 L1445.53 1720.96 L1445.25 1720.96 L1445.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1445.25,1720.96 1445.25,1720.96 1445.53,1720.96 1445.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1445.53 1720.96 L1445.53 1720.96 L1445.81 1720.96 L1445.81 1720.96 L1445.53 1720.96 L1445.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1445.53,1720.96 1445.53,1720.96 1445.81,1720.96 1445.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1445.81 1720.96 L1445.81 1720.96 L1446.1 1720.96 L1446.1 1720.96 L1445.81 1720.96 L1445.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1445.81,1720.96 1445.81,1720.96 1446.1,1720.96 1445.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1446.1 1720.96 L1446.1 1720.96 L1446.38 1720.96 L1446.38 1720.96 L1446.1 1720.96 L1446.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1446.1,1720.96 1446.1,1720.96 1446.38,1720.96 1446.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1446.38 1720.96 L1446.38 1720.96 L1446.66 1720.96 L1446.66 1720.96 L1446.38 1720.96 L1446.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1446.38,1720.96 1446.38,1720.96 1446.66,1720.96 1446.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1446.66 1720.96 L1446.66 1720.96 L1446.94 1720.96 L1446.94 1720.96 L1446.66 1720.96 L1446.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1446.66,1720.96 1446.66,1720.96 1446.94,1720.96 1446.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1446.94 1720.96 L1446.94 1720.96 L1447.22 1720.96 L1447.22 1720.96 L1446.94 1720.96 L1446.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1446.94,1720.96 1446.94,1720.96 1447.22,1720.96 1446.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1447.22 1720.96 L1447.22 1720.96 L1447.5 1720.96 L1447.5 1720.96 L1447.22 1720.96 L1447.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1447.22,1720.96 1447.22,1720.96 1447.5,1720.96 1447.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1447.5 1720.96 L1447.5 1720.96 L1447.79 1720.96 L1447.79 1720.96 L1447.5 1720.96 L1447.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1447.5,1720.96 1447.5,1720.96 1447.79,1720.96 1447.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1447.79 1720.96 L1447.79 1720.96 L1448.07 1720.96 L1448.07 1720.96 L1447.79 1720.96 L1447.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1447.79,1720.96 1447.79,1720.96 1448.07,1720.96 1447.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1448.07 1720.96 L1448.07 1720.96 L1448.35 1720.96 L1448.35 1720.96 L1448.07 1720.96 L1448.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1448.07,1720.96 1448.07,1720.96 1448.35,1720.96 1448.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1448.35 1720.96 L1448.35 1720.96 L1448.63 1720.96 L1448.63 1720.96 L1448.35 1720.96 L1448.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1448.35,1720.96 1448.35,1720.96 1448.63,1720.96 1448.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1448.63 1720.96 L1448.63 1720.96 L1448.91 1720.96 L1448.91 1720.96 L1448.63 1720.96 L1448.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1448.63,1720.96 1448.63,1720.96 1448.91,1720.96 1448.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1448.91 1720.96 L1448.91 1720.96 L1449.19 1720.96 L1449.19 1720.96 L1448.91 1720.96 L1448.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1448.91,1720.96 1448.91,1720.96 1449.19,1720.96 1448.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1449.19 1720.96 L1449.19 1720.96 L1449.48 1720.96 L1449.48 1720.96 L1449.19 1720.96 L1449.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1449.19,1720.96 1449.19,1720.96 1449.48,1720.96 1449.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1449.48 1720.96 L1449.48 1720.96 L1449.76 1720.96 L1449.76 1720.96 L1449.48 1720.96 L1449.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1449.48,1720.96 1449.48,1720.96 1449.76,1720.96 1449.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1449.76 1720.96 L1449.76 1720.96 L1450.04 1720.96 L1450.04 1720.96 L1449.76 1720.96 L1449.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1449.76,1720.96 1449.76,1720.96 1450.04,1720.96 1449.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1450.04 1720.96 L1450.04 1720.96 L1450.32 1720.96 L1450.32 1720.96 L1450.04 1720.96 L1450.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1450.04,1720.96 1450.04,1720.96 1450.32,1720.96 1450.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1450.32 1720.96 L1450.32 1720.96 L1450.6 1720.96 L1450.6 1720.96 L1450.32 1720.96 L1450.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1450.32,1720.96 1450.32,1720.96 1450.6,1720.96 1450.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1450.6 1720.96 L1450.6 1720.96 L1450.88 1720.96 L1450.88 1720.96 L1450.6 1720.96 L1450.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1450.6,1720.96 1450.6,1720.96 1450.88,1720.96 1450.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1450.88 1720.96 L1450.88 1720.96 L1451.17 1720.96 L1451.17 1720.96 L1450.88 1720.96 L1450.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1450.88,1720.96 1450.88,1720.96 1451.17,1720.96 1450.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1451.17 1720.96 L1451.17 1720.96 L1451.45 1720.96 L1451.45 1720.96 L1451.17 1720.96 L1451.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1451.17,1720.96 1451.17,1720.96 1451.45,1720.96 1451.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1451.45 1720.96 L1451.45 1720.96 L1451.73 1720.96 L1451.73 1720.96 L1451.45 1720.96 L1451.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1451.45,1720.96 1451.45,1720.96 1451.73,1720.96 1451.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1451.73 1720.96 L1451.73 1720.96 L1452.01 1720.96 L1452.01 1720.96 L1451.73 1720.96 L1451.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1451.73,1720.96 1451.73,1720.96 1452.01,1720.96 1451.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1452.01 1720.96 L1452.01 1720.96 L1452.29 1720.96 L1452.29 1720.96 L1452.01 1720.96 L1452.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1452.01,1720.96 1452.01,1720.96 1452.29,1720.96 1452.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1452.29 1720.96 L1452.29 1720.96 L1452.58 1720.96 L1452.58 1720.96 L1452.29 1720.96 L1452.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1452.29,1720.96 1452.29,1720.96 1452.58,1720.96 1452.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1452.58 1720.96 L1452.58 1720.96 L1452.86 1720.96 L1452.86 1720.96 L1452.58 1720.96 L1452.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1452.58,1720.96 1452.58,1720.96 1452.86,1720.96 1452.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1452.86 1720.96 L1452.86 1720.96 L1453.14 1720.96 L1453.14 1720.96 L1452.86 1720.96 L1452.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1452.86,1720.96 1452.86,1720.96 1453.14,1720.96 1452.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1453.14 1720.96 L1453.14 1720.96 L1453.42 1720.96 L1453.42 1720.96 L1453.14 1720.96 L1453.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1453.14,1720.96 1453.14,1720.96 1453.42,1720.96 1453.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1453.42 1720.96 L1453.42 1720.96 L1453.7 1720.96 L1453.7 1720.96 L1453.42 1720.96 L1453.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1453.42,1720.96 1453.42,1720.96 1453.7,1720.96 1453.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1453.7 1720.96 L1453.7 1720.96 L1453.98 1720.96 L1453.98 1720.96 L1453.7 1720.96 L1453.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1453.7,1720.96 1453.7,1720.96 1453.98,1720.96 1453.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1453.98 1720.96 L1453.98 1720.96 L1454.27 1720.96 L1454.27 1720.96 L1453.98 1720.96 L1453.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1453.98,1720.96 1453.98,1720.96 1454.27,1720.96 1453.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1454.27 1720.96 L1454.27 1720.96 L1454.55 1720.96 L1454.55 1720.96 L1454.27 1720.96 L1454.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1454.27,1720.96 1454.27,1720.96 1454.55,1720.96 1454.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1454.55 1720.96 L1454.55 1720.96 L1454.83 1720.96 L1454.83 1720.96 L1454.55 1720.96 L1454.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1454.55,1720.96 1454.55,1720.96 1454.83,1720.96 1454.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1454.83 1720.96 L1454.83 1720.96 L1455.11 1720.96 L1455.11 1720.96 L1454.83 1720.96 L1454.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1454.83,1720.96 1454.83,1720.96 1455.11,1720.96 1454.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1455.11 1720.96 L1455.11 1720.96 L1455.39 1720.96 L1455.39 1720.96 L1455.11 1720.96 L1455.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1455.11,1720.96 1455.11,1720.96 1455.39,1720.96 1455.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1455.39 1720.96 L1455.39 1720.96 L1455.67 1720.96 L1455.67 1720.96 L1455.39 1720.96 L1455.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1455.39,1720.96 1455.39,1720.96 1455.67,1720.96 1455.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1455.67 1720.76 L1455.67 1720.96 L1455.96 1720.96 L1455.96 1720.76 L1455.67 1720.76 L1455.67 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1455.67,1720.76 1455.67,1720.96 1455.96,1720.96 1455.96,1720.76 1455.67,1720.76 "/>
<path clip-path="url(#clip322)" d="M1455.96 1720.96 L1455.96 1720.96 L1456.24 1720.96 L1456.24 1720.96 L1455.96 1720.96 L1455.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1455.96,1720.96 1455.96,1720.96 1456.24,1720.96 1455.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1456.24 1720.96 L1456.24 1720.96 L1456.52 1720.96 L1456.52 1720.96 L1456.24 1720.96 L1456.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1456.24,1720.96 1456.24,1720.96 1456.52,1720.96 1456.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1456.52 1720.96 L1456.52 1720.96 L1456.8 1720.96 L1456.8 1720.96 L1456.52 1720.96 L1456.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1456.52,1720.96 1456.52,1720.96 1456.8,1720.96 1456.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1456.8 1720.96 L1456.8 1720.96 L1457.08 1720.96 L1457.08 1720.96 L1456.8 1720.96 L1456.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1456.8,1720.96 1456.8,1720.96 1457.08,1720.96 1456.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1457.08 1720.96 L1457.08 1720.96 L1457.36 1720.96 L1457.36 1720.96 L1457.08 1720.96 L1457.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1457.08,1720.96 1457.08,1720.96 1457.36,1720.96 1457.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1457.36 1720.96 L1457.36 1720.96 L1457.65 1720.96 L1457.65 1720.96 L1457.36 1720.96 L1457.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1457.36,1720.96 1457.36,1720.96 1457.65,1720.96 1457.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1457.65 1720.96 L1457.65 1720.96 L1457.93 1720.96 L1457.93 1720.96 L1457.65 1720.96 L1457.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1457.65,1720.96 1457.65,1720.96 1457.93,1720.96 1457.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1457.93 1720.96 L1457.93 1720.96 L1458.21 1720.96 L1458.21 1720.96 L1457.93 1720.96 L1457.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1457.93,1720.96 1457.93,1720.96 1458.21,1720.96 1457.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1458.21 1720.96 L1458.21 1720.96 L1458.49 1720.96 L1458.49 1720.96 L1458.21 1720.96 L1458.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1458.21,1720.96 1458.21,1720.96 1458.49,1720.96 1458.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1458.49 1720.96 L1458.49 1720.96 L1458.77 1720.96 L1458.77 1720.96 L1458.49 1720.96 L1458.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1458.49,1720.96 1458.49,1720.96 1458.77,1720.96 1458.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1458.77 1720.96 L1458.77 1720.96 L1459.05 1720.96 L1459.05 1720.96 L1458.77 1720.96 L1458.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1458.77,1720.96 1458.77,1720.96 1459.05,1720.96 1458.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1459.05 1720.96 L1459.05 1720.96 L1459.34 1720.96 L1459.34 1720.96 L1459.05 1720.96 L1459.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1459.05,1720.96 1459.05,1720.96 1459.34,1720.96 1459.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1459.34 1720.96 L1459.34 1720.96 L1459.62 1720.96 L1459.62 1720.96 L1459.34 1720.96 L1459.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1459.34,1720.96 1459.34,1720.96 1459.62,1720.96 1459.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1459.62 1720.96 L1459.62 1720.96 L1459.9 1720.96 L1459.9 1720.96 L1459.62 1720.96 L1459.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1459.62,1720.96 1459.62,1720.96 1459.9,1720.96 1459.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1459.9 1720.96 L1459.9 1720.96 L1460.18 1720.96 L1460.18 1720.96 L1459.9 1720.96 L1459.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1459.9,1720.96 1459.9,1720.96 1460.18,1720.96 1459.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1460.18 1720.96 L1460.18 1720.96 L1460.46 1720.96 L1460.46 1720.96 L1460.18 1720.96 L1460.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1460.18,1720.96 1460.18,1720.96 1460.46,1720.96 1460.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1460.46 1720.96 L1460.46 1720.96 L1460.75 1720.96 L1460.75 1720.96 L1460.46 1720.96 L1460.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1460.46,1720.96 1460.46,1720.96 1460.75,1720.96 1460.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1460.75 1720.96 L1460.75 1720.96 L1461.03 1720.96 L1461.03 1720.96 L1460.75 1720.96 L1460.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1460.75,1720.96 1460.75,1720.96 1461.03,1720.96 1460.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1461.03 1720.96 L1461.03 1720.96 L1461.31 1720.96 L1461.31 1720.96 L1461.03 1720.96 L1461.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1461.03,1720.96 1461.03,1720.96 1461.31,1720.96 1461.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1461.31 1720.96 L1461.31 1720.96 L1461.59 1720.96 L1461.59 1720.96 L1461.31 1720.96 L1461.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1461.31,1720.96 1461.31,1720.96 1461.59,1720.96 1461.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1461.59 1720.96 L1461.59 1720.96 L1461.87 1720.96 L1461.87 1720.96 L1461.59 1720.96 L1461.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1461.59,1720.96 1461.59,1720.96 1461.87,1720.96 1461.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1461.87 1720.96 L1461.87 1720.96 L1462.15 1720.96 L1462.15 1720.96 L1461.87 1720.96 L1461.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1461.87,1720.96 1461.87,1720.96 1462.15,1720.96 1461.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1462.15 1720.96 L1462.15 1720.96 L1462.44 1720.96 L1462.44 1720.96 L1462.15 1720.96 L1462.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1462.15,1720.96 1462.15,1720.96 1462.44,1720.96 1462.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1462.44 1720.96 L1462.44 1720.96 L1462.72 1720.96 L1462.72 1720.96 L1462.44 1720.96 L1462.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1462.44,1720.96 1462.44,1720.96 1462.72,1720.96 1462.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1462.72 1720.96 L1462.72 1720.96 L1463 1720.96 L1463 1720.96 L1462.72 1720.96 L1462.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1462.72,1720.96 1462.72,1720.96 1463,1720.96 1462.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1463 1720.96 L1463 1720.96 L1463.28 1720.96 L1463.28 1720.96 L1463 1720.96 L1463 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1463,1720.96 1463,1720.96 1463.28,1720.96 1463,1720.96 "/>
<path clip-path="url(#clip322)" d="M1463.28 1720.96 L1463.28 1720.96 L1463.56 1720.96 L1463.56 1720.96 L1463.28 1720.96 L1463.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1463.28,1720.96 1463.28,1720.96 1463.56,1720.96 1463.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1463.56 1720.96 L1463.56 1720.96 L1463.84 1720.96 L1463.84 1720.96 L1463.56 1720.96 L1463.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1463.56,1720.96 1463.56,1720.96 1463.84,1720.96 1463.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1463.84 1720.96 L1463.84 1720.96 L1464.13 1720.96 L1464.13 1720.96 L1463.84 1720.96 L1463.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1463.84,1720.96 1463.84,1720.96 1464.13,1720.96 1463.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1464.13 1720.96 L1464.13 1720.96 L1464.41 1720.96 L1464.41 1720.96 L1464.13 1720.96 L1464.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1464.13,1720.96 1464.13,1720.96 1464.41,1720.96 1464.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1464.41 1720.96 L1464.41 1720.96 L1464.69 1720.96 L1464.69 1720.96 L1464.41 1720.96 L1464.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1464.41,1720.96 1464.41,1720.96 1464.69,1720.96 1464.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1464.69 1720.96 L1464.69 1720.96 L1464.97 1720.96 L1464.97 1720.96 L1464.69 1720.96 L1464.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1464.69,1720.96 1464.69,1720.96 1464.97,1720.96 1464.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1464.97 1720.96 L1464.97 1720.96 L1465.25 1720.96 L1465.25 1720.96 L1464.97 1720.96 L1464.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1464.97,1720.96 1464.97,1720.96 1465.25,1720.96 1464.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1465.25 1720.96 L1465.25 1720.96 L1465.53 1720.96 L1465.53 1720.96 L1465.25 1720.96 L1465.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1465.25,1720.96 1465.25,1720.96 1465.53,1720.96 1465.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1465.53 1720.96 L1465.53 1720.96 L1465.82 1720.96 L1465.82 1720.96 L1465.53 1720.96 L1465.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1465.53,1720.96 1465.53,1720.96 1465.82,1720.96 1465.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1465.82 1720.96 L1465.82 1720.96 L1466.1 1720.96 L1466.1 1720.96 L1465.82 1720.96 L1465.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1465.82,1720.96 1465.82,1720.96 1466.1,1720.96 1465.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1466.1 1720.96 L1466.1 1720.96 L1466.38 1720.96 L1466.38 1720.96 L1466.1 1720.96 L1466.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1466.1,1720.96 1466.1,1720.96 1466.38,1720.96 1466.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1466.38 1720.96 L1466.38 1720.96 L1466.66 1720.96 L1466.66 1720.96 L1466.38 1720.96 L1466.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1466.38,1720.96 1466.38,1720.96 1466.66,1720.96 1466.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1466.66 1720.96 L1466.66 1720.96 L1466.94 1720.96 L1466.94 1720.96 L1466.66 1720.96 L1466.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1466.66,1720.96 1466.66,1720.96 1466.94,1720.96 1466.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1466.94 1720.96 L1466.94 1720.96 L1467.22 1720.96 L1467.22 1720.96 L1466.94 1720.96 L1466.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1466.94,1720.96 1466.94,1720.96 1467.22,1720.96 1466.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1467.22 1720.96 L1467.22 1720.96 L1467.51 1720.96 L1467.51 1720.96 L1467.22 1720.96 L1467.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1467.22,1720.96 1467.22,1720.96 1467.51,1720.96 1467.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1467.51 1720.96 L1467.51 1720.96 L1467.79 1720.96 L1467.79 1720.96 L1467.51 1720.96 L1467.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1467.51,1720.96 1467.51,1720.96 1467.79,1720.96 1467.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1467.79 1720.96 L1467.79 1720.96 L1468.07 1720.96 L1468.07 1720.96 L1467.79 1720.96 L1467.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1467.79,1720.96 1467.79,1720.96 1468.07,1720.96 1467.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1468.07 1720.96 L1468.07 1720.96 L1468.35 1720.96 L1468.35 1720.96 L1468.07 1720.96 L1468.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1468.07,1720.96 1468.07,1720.96 1468.35,1720.96 1468.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1468.35 1720.96 L1468.35 1720.96 L1468.63 1720.96 L1468.63 1720.96 L1468.35 1720.96 L1468.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1468.35,1720.96 1468.35,1720.96 1468.63,1720.96 1468.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1468.63 1720.96 L1468.63 1720.96 L1468.92 1720.96 L1468.92 1720.96 L1468.63 1720.96 L1468.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1468.63,1720.96 1468.63,1720.96 1468.92,1720.96 1468.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1468.92 1720.96 L1468.92 1720.96 L1469.2 1720.96 L1469.2 1720.96 L1468.92 1720.96 L1468.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1468.92,1720.96 1468.92,1720.96 1469.2,1720.96 1468.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1469.2 1720.96 L1469.2 1720.96 L1469.48 1720.96 L1469.48 1720.96 L1469.2 1720.96 L1469.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1469.2,1720.96 1469.2,1720.96 1469.48,1720.96 1469.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1469.48 1720.96 L1469.48 1720.96 L1469.76 1720.96 L1469.76 1720.96 L1469.48 1720.96 L1469.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1469.48,1720.96 1469.48,1720.96 1469.76,1720.96 1469.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1469.76 1720.96 L1469.76 1720.96 L1470.04 1720.96 L1470.04 1720.96 L1469.76 1720.96 L1469.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1469.76,1720.96 1469.76,1720.96 1470.04,1720.96 1469.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1470.04 1720.96 L1470.04 1720.96 L1470.32 1720.96 L1470.32 1720.96 L1470.04 1720.96 L1470.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1470.04,1720.96 1470.04,1720.96 1470.32,1720.96 1470.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1470.32 1720.96 L1470.32 1720.96 L1470.61 1720.96 L1470.61 1720.96 L1470.32 1720.96 L1470.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1470.32,1720.96 1470.32,1720.96 1470.61,1720.96 1470.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1470.61 1720.96 L1470.61 1720.96 L1470.89 1720.96 L1470.89 1720.96 L1470.61 1720.96 L1470.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1470.61,1720.96 1470.61,1720.96 1470.89,1720.96 1470.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1470.89 1720.96 L1470.89 1720.96 L1471.17 1720.96 L1471.17 1720.96 L1470.89 1720.96 L1470.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1470.89,1720.96 1470.89,1720.96 1471.17,1720.96 1470.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1471.17 1720.76 L1471.17 1720.96 L1471.45 1720.96 L1471.45 1720.76 L1471.17 1720.76 L1471.17 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1471.17,1720.76 1471.17,1720.96 1471.45,1720.96 1471.45,1720.76 1471.17,1720.76 "/>
<path clip-path="url(#clip322)" d="M1471.45 1720.96 L1471.45 1720.96 L1471.73 1720.96 L1471.73 1720.96 L1471.45 1720.96 L1471.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1471.45,1720.96 1471.45,1720.96 1471.73,1720.96 1471.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1471.73 1720.96 L1471.73 1720.96 L1472.01 1720.96 L1472.01 1720.96 L1471.73 1720.96 L1471.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1471.73,1720.96 1471.73,1720.96 1472.01,1720.96 1471.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1472.01 1720.96 L1472.01 1720.96 L1472.3 1720.96 L1472.3 1720.96 L1472.01 1720.96 L1472.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1472.01,1720.96 1472.01,1720.96 1472.3,1720.96 1472.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1472.3 1720.96 L1472.3 1720.96 L1472.58 1720.96 L1472.58 1720.96 L1472.3 1720.96 L1472.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1472.3,1720.96 1472.3,1720.96 1472.58,1720.96 1472.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1472.58 1720.96 L1472.58 1720.96 L1472.86 1720.96 L1472.86 1720.96 L1472.58 1720.96 L1472.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1472.58,1720.96 1472.58,1720.96 1472.86,1720.96 1472.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1472.86 1720.96 L1472.86 1720.96 L1473.14 1720.96 L1473.14 1720.96 L1472.86 1720.96 L1472.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1472.86,1720.96 1472.86,1720.96 1473.14,1720.96 1472.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1473.14 1720.96 L1473.14 1720.96 L1473.42 1720.96 L1473.42 1720.96 L1473.14 1720.96 L1473.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1473.14,1720.96 1473.14,1720.96 1473.42,1720.96 1473.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1473.42 1720.96 L1473.42 1720.96 L1473.7 1720.96 L1473.7 1720.96 L1473.42 1720.96 L1473.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1473.42,1720.96 1473.42,1720.96 1473.7,1720.96 1473.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1473.7 1720.96 L1473.7 1720.96 L1473.99 1720.96 L1473.99 1720.96 L1473.7 1720.96 L1473.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1473.7,1720.96 1473.7,1720.96 1473.99,1720.96 1473.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1473.99 1720.96 L1473.99 1720.96 L1474.27 1720.96 L1474.27 1720.96 L1473.99 1720.96 L1473.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1473.99,1720.96 1473.99,1720.96 1474.27,1720.96 1473.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1474.27 1720.96 L1474.27 1720.96 L1474.55 1720.96 L1474.55 1720.96 L1474.27 1720.96 L1474.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1474.27,1720.96 1474.27,1720.96 1474.55,1720.96 1474.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1474.55 1720.96 L1474.55 1720.96 L1474.83 1720.96 L1474.83 1720.96 L1474.55 1720.96 L1474.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1474.55,1720.96 1474.55,1720.96 1474.83,1720.96 1474.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1474.83 1720.96 L1474.83 1720.96 L1475.11 1720.96 L1475.11 1720.96 L1474.83 1720.96 L1474.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1474.83,1720.96 1474.83,1720.96 1475.11,1720.96 1474.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1475.11 1720.96 L1475.11 1720.96 L1475.39 1720.96 L1475.39 1720.96 L1475.11 1720.96 L1475.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1475.11,1720.96 1475.11,1720.96 1475.39,1720.96 1475.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1475.39 1720.96 L1475.39 1720.96 L1475.68 1720.96 L1475.68 1720.96 L1475.39 1720.96 L1475.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1475.39,1720.96 1475.39,1720.96 1475.68,1720.96 1475.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1475.68 1720.96 L1475.68 1720.96 L1475.96 1720.96 L1475.96 1720.96 L1475.68 1720.96 L1475.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1475.68,1720.96 1475.68,1720.96 1475.96,1720.96 1475.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1475.96 1720.96 L1475.96 1720.96 L1476.24 1720.96 L1476.24 1720.96 L1475.96 1720.96 L1475.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1475.96,1720.96 1475.96,1720.96 1476.24,1720.96 1475.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1476.24 1720.96 L1476.24 1720.96 L1476.52 1720.96 L1476.52 1720.96 L1476.24 1720.96 L1476.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1476.24,1720.96 1476.24,1720.96 1476.52,1720.96 1476.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1476.52 1720.96 L1476.52 1720.96 L1476.8 1720.96 L1476.8 1720.96 L1476.52 1720.96 L1476.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1476.52,1720.96 1476.52,1720.96 1476.8,1720.96 1476.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1476.8 1720.96 L1476.8 1720.96 L1477.09 1720.96 L1477.09 1720.96 L1476.8 1720.96 L1476.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1476.8,1720.96 1476.8,1720.96 1477.09,1720.96 1476.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1477.09 1720.96 L1477.09 1720.96 L1477.37 1720.96 L1477.37 1720.96 L1477.09 1720.96 L1477.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1477.09,1720.96 1477.09,1720.96 1477.37,1720.96 1477.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1477.37 1720.96 L1477.37 1720.96 L1477.65 1720.96 L1477.65 1720.96 L1477.37 1720.96 L1477.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1477.37,1720.96 1477.37,1720.96 1477.65,1720.96 1477.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1477.65 1720.96 L1477.65 1720.96 L1477.93 1720.96 L1477.93 1720.96 L1477.65 1720.96 L1477.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1477.65,1720.96 1477.65,1720.96 1477.93,1720.96 1477.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1477.93 1720.96 L1477.93 1720.96 L1478.21 1720.96 L1478.21 1720.96 L1477.93 1720.96 L1477.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1477.93,1720.96 1477.93,1720.96 1478.21,1720.96 1477.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1478.21 1720.96 L1478.21 1720.96 L1478.49 1720.96 L1478.49 1720.96 L1478.21 1720.96 L1478.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1478.21,1720.96 1478.21,1720.96 1478.49,1720.96 1478.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1478.49 1720.96 L1478.49 1720.96 L1478.78 1720.96 L1478.78 1720.96 L1478.49 1720.96 L1478.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1478.49,1720.96 1478.49,1720.96 1478.78,1720.96 1478.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1478.78 1720.96 L1478.78 1720.96 L1479.06 1720.96 L1479.06 1720.96 L1478.78 1720.96 L1478.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1478.78,1720.96 1478.78,1720.96 1479.06,1720.96 1478.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1479.06 1720.96 L1479.06 1720.96 L1479.34 1720.96 L1479.34 1720.96 L1479.06 1720.96 L1479.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1479.06,1720.96 1479.06,1720.96 1479.34,1720.96 1479.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1479.34 1720.96 L1479.34 1720.96 L1479.62 1720.96 L1479.62 1720.96 L1479.34 1720.96 L1479.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1479.34,1720.96 1479.34,1720.96 1479.62,1720.96 1479.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1479.62 1720.96 L1479.62 1720.96 L1479.9 1720.96 L1479.9 1720.96 L1479.62 1720.96 L1479.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1479.62,1720.96 1479.62,1720.96 1479.9,1720.96 1479.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1479.9 1720.76 L1479.9 1720.96 L1480.18 1720.96 L1480.18 1720.76 L1479.9 1720.76 L1479.9 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1479.9,1720.76 1479.9,1720.96 1480.18,1720.96 1480.18,1720.76 1479.9,1720.76 "/>
<path clip-path="url(#clip322)" d="M1480.18 1720.96 L1480.18 1720.96 L1480.47 1720.96 L1480.47 1720.96 L1480.18 1720.96 L1480.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1480.18,1720.96 1480.18,1720.96 1480.47,1720.96 1480.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1480.47 1720.76 L1480.47 1720.96 L1480.75 1720.96 L1480.75 1720.76 L1480.47 1720.76 L1480.47 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1480.47,1720.76 1480.47,1720.96 1480.75,1720.96 1480.75,1720.76 1480.47,1720.76 "/>
<path clip-path="url(#clip322)" d="M1480.75 1720.96 L1480.75 1720.96 L1481.03 1720.96 L1481.03 1720.96 L1480.75 1720.96 L1480.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1480.75,1720.96 1480.75,1720.96 1481.03,1720.96 1480.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1481.03 1720.96 L1481.03 1720.96 L1481.31 1720.96 L1481.31 1720.96 L1481.03 1720.96 L1481.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1481.03,1720.96 1481.03,1720.96 1481.31,1720.96 1481.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1481.31 1720.96 L1481.31 1720.96 L1481.59 1720.96 L1481.59 1720.96 L1481.31 1720.96 L1481.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1481.31,1720.96 1481.31,1720.96 1481.59,1720.96 1481.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1481.59 1720.96 L1481.59 1720.96 L1481.87 1720.96 L1481.87 1720.96 L1481.59 1720.96 L1481.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1481.59,1720.96 1481.59,1720.96 1481.87,1720.96 1481.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1481.87 1720.96 L1481.87 1720.96 L1482.16 1720.96 L1482.16 1720.96 L1481.87 1720.96 L1481.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1481.87,1720.96 1481.87,1720.96 1482.16,1720.96 1481.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1482.16 1720.96 L1482.16 1720.96 L1482.44 1720.96 L1482.44 1720.96 L1482.16 1720.96 L1482.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1482.16,1720.96 1482.16,1720.96 1482.44,1720.96 1482.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1482.44 1720.96 L1482.44 1720.96 L1482.72 1720.96 L1482.72 1720.96 L1482.44 1720.96 L1482.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1482.44,1720.96 1482.44,1720.96 1482.72,1720.96 1482.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1482.72 1720.96 L1482.72 1720.96 L1483 1720.96 L1483 1720.96 L1482.72 1720.96 L1482.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1482.72,1720.96 1482.72,1720.96 1483,1720.96 1482.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1483 1720.96 L1483 1720.96 L1483.28 1720.96 L1483.28 1720.96 L1483 1720.96 L1483 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1483,1720.96 1483,1720.96 1483.28,1720.96 1483,1720.96 "/>
<path clip-path="url(#clip322)" d="M1483.28 1720.96 L1483.28 1720.96 L1483.56 1720.96 L1483.56 1720.96 L1483.28 1720.96 L1483.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1483.28,1720.96 1483.28,1720.96 1483.56,1720.96 1483.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1483.56 1720.96 L1483.56 1720.96 L1483.85 1720.96 L1483.85 1720.96 L1483.56 1720.96 L1483.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1483.56,1720.96 1483.56,1720.96 1483.85,1720.96 1483.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1483.85 1720.76 L1483.85 1720.96 L1484.13 1720.96 L1484.13 1720.76 L1483.85 1720.76 L1483.85 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1483.85,1720.76 1483.85,1720.96 1484.13,1720.96 1484.13,1720.76 1483.85,1720.76 "/>
<path clip-path="url(#clip322)" d="M1484.13 1720.96 L1484.13 1720.96 L1484.41 1720.96 L1484.41 1720.96 L1484.13 1720.96 L1484.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1484.13,1720.96 1484.13,1720.96 1484.41,1720.96 1484.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1484.41 1720.96 L1484.41 1720.96 L1484.69 1720.96 L1484.69 1720.96 L1484.41 1720.96 L1484.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1484.41,1720.96 1484.41,1720.96 1484.69,1720.96 1484.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1484.69 1720.96 L1484.69 1720.96 L1484.97 1720.96 L1484.97 1720.96 L1484.69 1720.96 L1484.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1484.69,1720.96 1484.69,1720.96 1484.97,1720.96 1484.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1484.97 1720.96 L1484.97 1720.96 L1485.26 1720.96 L1485.26 1720.96 L1484.97 1720.96 L1484.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1484.97,1720.96 1484.97,1720.96 1485.26,1720.96 1484.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1485.26 1720.96 L1485.26 1720.96 L1485.54 1720.96 L1485.54 1720.96 L1485.26 1720.96 L1485.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1485.26,1720.96 1485.26,1720.96 1485.54,1720.96 1485.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1485.54 1720.96 L1485.54 1720.96 L1485.82 1720.96 L1485.82 1720.96 L1485.54 1720.96 L1485.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1485.54,1720.96 1485.54,1720.96 1485.82,1720.96 1485.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1485.82 1720.96 L1485.82 1720.96 L1486.1 1720.96 L1486.1 1720.96 L1485.82 1720.96 L1485.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1485.82,1720.96 1485.82,1720.96 1486.1,1720.96 1485.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1486.1 1720.96 L1486.1 1720.96 L1486.38 1720.96 L1486.38 1720.96 L1486.1 1720.96 L1486.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1486.1,1720.96 1486.1,1720.96 1486.38,1720.96 1486.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1486.38 1720.96 L1486.38 1720.96 L1486.66 1720.96 L1486.66 1720.96 L1486.38 1720.96 L1486.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1486.38,1720.96 1486.38,1720.96 1486.66,1720.96 1486.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1486.66 1720.96 L1486.66 1720.96 L1486.95 1720.96 L1486.95 1720.96 L1486.66 1720.96 L1486.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1486.66,1720.96 1486.66,1720.96 1486.95,1720.96 1486.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1486.95 1720.96 L1486.95 1720.96 L1487.23 1720.96 L1487.23 1720.96 L1486.95 1720.96 L1486.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1486.95,1720.96 1486.95,1720.96 1487.23,1720.96 1486.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1487.23 1720.96 L1487.23 1720.96 L1487.51 1720.96 L1487.51 1720.96 L1487.23 1720.96 L1487.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1487.23,1720.96 1487.23,1720.96 1487.51,1720.96 1487.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1487.51 1720.96 L1487.51 1720.96 L1487.79 1720.96 L1487.79 1720.96 L1487.51 1720.96 L1487.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1487.51,1720.96 1487.51,1720.96 1487.79,1720.96 1487.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1487.79 1720.96 L1487.79 1720.96 L1488.07 1720.96 L1488.07 1720.96 L1487.79 1720.96 L1487.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1487.79,1720.96 1487.79,1720.96 1488.07,1720.96 1487.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1488.07 1720.96 L1488.07 1720.96 L1488.35 1720.96 L1488.35 1720.96 L1488.07 1720.96 L1488.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1488.07,1720.96 1488.07,1720.96 1488.35,1720.96 1488.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1488.35 1720.96 L1488.35 1720.96 L1488.64 1720.96 L1488.64 1720.96 L1488.35 1720.96 L1488.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1488.35,1720.96 1488.35,1720.96 1488.64,1720.96 1488.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1488.64 1720.96 L1488.64 1720.96 L1488.92 1720.96 L1488.92 1720.96 L1488.64 1720.96 L1488.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1488.64,1720.96 1488.64,1720.96 1488.92,1720.96 1488.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1488.92 1720.96 L1488.92 1720.96 L1489.2 1720.96 L1489.2 1720.96 L1488.92 1720.96 L1488.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1488.92,1720.96 1488.92,1720.96 1489.2,1720.96 1488.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1489.2 1720.96 L1489.2 1720.96 L1489.48 1720.96 L1489.48 1720.96 L1489.2 1720.96 L1489.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1489.2,1720.96 1489.2,1720.96 1489.48,1720.96 1489.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1489.48 1720.96 L1489.48 1720.96 L1489.76 1720.96 L1489.76 1720.96 L1489.48 1720.96 L1489.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1489.48,1720.96 1489.48,1720.96 1489.76,1720.96 1489.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1489.76 1720.96 L1489.76 1720.96 L1490.04 1720.96 L1490.04 1720.96 L1489.76 1720.96 L1489.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1489.76,1720.96 1489.76,1720.96 1490.04,1720.96 1489.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1490.04 1720.96 L1490.04 1720.96 L1490.33 1720.96 L1490.33 1720.96 L1490.04 1720.96 L1490.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1490.04,1720.96 1490.04,1720.96 1490.33,1720.96 1490.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1490.33 1720.96 L1490.33 1720.96 L1490.61 1720.96 L1490.61 1720.96 L1490.33 1720.96 L1490.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1490.33,1720.96 1490.33,1720.96 1490.61,1720.96 1490.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1490.61 1720.96 L1490.61 1720.96 L1490.89 1720.96 L1490.89 1720.96 L1490.61 1720.96 L1490.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1490.61,1720.96 1490.61,1720.96 1490.89,1720.96 1490.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1490.89 1720.96 L1490.89 1720.96 L1491.17 1720.96 L1491.17 1720.96 L1490.89 1720.96 L1490.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1490.89,1720.96 1490.89,1720.96 1491.17,1720.96 1490.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1491.17 1720.96 L1491.17 1720.96 L1491.45 1720.96 L1491.45 1720.96 L1491.17 1720.96 L1491.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1491.17,1720.96 1491.17,1720.96 1491.45,1720.96 1491.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1491.45 1720.96 L1491.45 1720.96 L1491.73 1720.96 L1491.73 1720.96 L1491.45 1720.96 L1491.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1491.45,1720.96 1491.45,1720.96 1491.73,1720.96 1491.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1491.73 1720.96 L1491.73 1720.96 L1492.02 1720.96 L1492.02 1720.96 L1491.73 1720.96 L1491.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1491.73,1720.96 1491.73,1720.96 1492.02,1720.96 1491.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1492.02 1720.96 L1492.02 1720.96 L1492.3 1720.96 L1492.3 1720.96 L1492.02 1720.96 L1492.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1492.02,1720.96 1492.02,1720.96 1492.3,1720.96 1492.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1492.3 1720.96 L1492.3 1720.96 L1492.58 1720.96 L1492.58 1720.96 L1492.3 1720.96 L1492.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1492.3,1720.96 1492.3,1720.96 1492.58,1720.96 1492.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1492.58 1720.96 L1492.58 1720.96 L1492.86 1720.96 L1492.86 1720.96 L1492.58 1720.96 L1492.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1492.58,1720.96 1492.58,1720.96 1492.86,1720.96 1492.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1492.86 1720.96 L1492.86 1720.96 L1493.14 1720.96 L1493.14 1720.96 L1492.86 1720.96 L1492.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1492.86,1720.96 1492.86,1720.96 1493.14,1720.96 1492.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1493.14 1720.96 L1493.14 1720.96 L1493.43 1720.96 L1493.43 1720.96 L1493.14 1720.96 L1493.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1493.14,1720.96 1493.14,1720.96 1493.43,1720.96 1493.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1493.43 1720.96 L1493.43 1720.96 L1493.71 1720.96 L1493.71 1720.96 L1493.43 1720.96 L1493.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1493.43,1720.96 1493.43,1720.96 1493.71,1720.96 1493.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1493.71 1720.96 L1493.71 1720.96 L1493.99 1720.96 L1493.99 1720.96 L1493.71 1720.96 L1493.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1493.71,1720.96 1493.71,1720.96 1493.99,1720.96 1493.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1493.99 1720.96 L1493.99 1720.96 L1494.27 1720.96 L1494.27 1720.96 L1493.99 1720.96 L1493.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1493.99,1720.96 1493.99,1720.96 1494.27,1720.96 1493.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1494.27 1720.96 L1494.27 1720.96 L1494.55 1720.96 L1494.55 1720.96 L1494.27 1720.96 L1494.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1494.27,1720.96 1494.27,1720.96 1494.55,1720.96 1494.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1494.55 1720.96 L1494.55 1720.96 L1494.83 1720.96 L1494.83 1720.96 L1494.55 1720.96 L1494.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1494.55,1720.96 1494.55,1720.96 1494.83,1720.96 1494.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1494.83 1720.96 L1494.83 1720.96 L1495.12 1720.96 L1495.12 1720.96 L1494.83 1720.96 L1494.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1494.83,1720.96 1494.83,1720.96 1495.12,1720.96 1494.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1495.12 1720.96 L1495.12 1720.96 L1495.4 1720.96 L1495.4 1720.96 L1495.12 1720.96 L1495.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1495.12,1720.96 1495.12,1720.96 1495.4,1720.96 1495.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1495.4 1720.96 L1495.4 1720.96 L1495.68 1720.96 L1495.68 1720.96 L1495.4 1720.96 L1495.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1495.4,1720.96 1495.4,1720.96 1495.68,1720.96 1495.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1495.68 1720.96 L1495.68 1720.96 L1495.96 1720.96 L1495.96 1720.96 L1495.68 1720.96 L1495.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1495.68,1720.96 1495.68,1720.96 1495.96,1720.96 1495.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1495.96 1720.96 L1495.96 1720.96 L1496.24 1720.96 L1496.24 1720.96 L1495.96 1720.96 L1495.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1495.96,1720.96 1495.96,1720.96 1496.24,1720.96 1495.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1496.24 1720.96 L1496.24 1720.96 L1496.52 1720.96 L1496.52 1720.96 L1496.24 1720.96 L1496.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1496.24,1720.96 1496.24,1720.96 1496.52,1720.96 1496.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1496.52 1720.96 L1496.52 1720.96 L1496.81 1720.96 L1496.81 1720.96 L1496.52 1720.96 L1496.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1496.52,1720.96 1496.52,1720.96 1496.81,1720.96 1496.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1496.81 1720.96 L1496.81 1720.96 L1497.09 1720.96 L1497.09 1720.96 L1496.81 1720.96 L1496.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1496.81,1720.96 1496.81,1720.96 1497.09,1720.96 1496.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1497.09 1720.96 L1497.09 1720.96 L1497.37 1720.96 L1497.37 1720.96 L1497.09 1720.96 L1497.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1497.09,1720.96 1497.09,1720.96 1497.37,1720.96 1497.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1497.37 1720.96 L1497.37 1720.96 L1497.65 1720.96 L1497.65 1720.96 L1497.37 1720.96 L1497.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1497.37,1720.96 1497.37,1720.96 1497.65,1720.96 1497.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1497.65 1720.96 L1497.65 1720.96 L1497.93 1720.96 L1497.93 1720.96 L1497.65 1720.96 L1497.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1497.65,1720.96 1497.65,1720.96 1497.93,1720.96 1497.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1497.93 1720.96 L1497.93 1720.96 L1498.21 1720.96 L1498.21 1720.96 L1497.93 1720.96 L1497.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1497.93,1720.96 1497.93,1720.96 1498.21,1720.96 1497.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1498.21 1720.96 L1498.21 1720.96 L1498.5 1720.96 L1498.5 1720.96 L1498.21 1720.96 L1498.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1498.21,1720.96 1498.21,1720.96 1498.5,1720.96 1498.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1498.5 1720.96 L1498.5 1720.96 L1498.78 1720.96 L1498.78 1720.96 L1498.5 1720.96 L1498.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1498.5,1720.96 1498.5,1720.96 1498.78,1720.96 1498.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1498.78 1720.96 L1498.78 1720.96 L1499.06 1720.96 L1499.06 1720.96 L1498.78 1720.96 L1498.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1498.78,1720.96 1498.78,1720.96 1499.06,1720.96 1498.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1499.06 1720.96 L1499.06 1720.96 L1499.34 1720.96 L1499.34 1720.96 L1499.06 1720.96 L1499.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1499.06,1720.96 1499.06,1720.96 1499.34,1720.96 1499.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1499.34 1720.96 L1499.34 1720.96 L1499.62 1720.96 L1499.62 1720.96 L1499.34 1720.96 L1499.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1499.34,1720.96 1499.34,1720.96 1499.62,1720.96 1499.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1499.62 1720.76 L1499.62 1720.96 L1499.9 1720.96 L1499.9 1720.76 L1499.62 1720.76 L1499.62 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1499.62,1720.76 1499.62,1720.96 1499.9,1720.96 1499.9,1720.76 1499.62,1720.76 "/>
<path clip-path="url(#clip322)" d="M1499.9 1720.96 L1499.9 1720.96 L1500.19 1720.96 L1500.19 1720.96 L1499.9 1720.96 L1499.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1499.9,1720.96 1499.9,1720.96 1500.19,1720.96 1499.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1500.19 1720.96 L1500.19 1720.96 L1500.47 1720.96 L1500.47 1720.96 L1500.19 1720.96 L1500.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1500.19,1720.96 1500.19,1720.96 1500.47,1720.96 1500.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1500.47 1720.96 L1500.47 1720.96 L1500.75 1720.96 L1500.75 1720.96 L1500.47 1720.96 L1500.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1500.47,1720.96 1500.47,1720.96 1500.75,1720.96 1500.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1500.75 1720.96 L1500.75 1720.96 L1501.03 1720.96 L1501.03 1720.96 L1500.75 1720.96 L1500.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1500.75,1720.96 1500.75,1720.96 1501.03,1720.96 1500.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1501.03 1720.96 L1501.03 1720.96 L1501.31 1720.96 L1501.31 1720.96 L1501.03 1720.96 L1501.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1501.03,1720.96 1501.03,1720.96 1501.31,1720.96 1501.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1501.31 1720.96 L1501.31 1720.96 L1501.6 1720.96 L1501.6 1720.96 L1501.31 1720.96 L1501.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1501.31,1720.96 1501.31,1720.96 1501.6,1720.96 1501.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1501.6 1720.96 L1501.6 1720.96 L1501.88 1720.96 L1501.88 1720.96 L1501.6 1720.96 L1501.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1501.6,1720.96 1501.6,1720.96 1501.88,1720.96 1501.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1501.88 1720.96 L1501.88 1720.96 L1502.16 1720.96 L1502.16 1720.96 L1501.88 1720.96 L1501.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1501.88,1720.96 1501.88,1720.96 1502.16,1720.96 1501.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1502.16 1720.96 L1502.16 1720.96 L1502.44 1720.96 L1502.44 1720.96 L1502.16 1720.96 L1502.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1502.16,1720.96 1502.16,1720.96 1502.44,1720.96 1502.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1502.44 1720.96 L1502.44 1720.96 L1502.72 1720.96 L1502.72 1720.96 L1502.44 1720.96 L1502.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1502.44,1720.96 1502.44,1720.96 1502.72,1720.96 1502.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1502.72 1720.96 L1502.72 1720.96 L1503 1720.96 L1503 1720.96 L1502.72 1720.96 L1502.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1502.72,1720.96 1502.72,1720.96 1503,1720.96 1502.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1503 1720.76 L1503 1720.96 L1503.29 1720.96 L1503.29 1720.76 L1503 1720.76 L1503 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1503,1720.76 1503,1720.96 1503.29,1720.96 1503.29,1720.76 1503,1720.76 "/>
<path clip-path="url(#clip322)" d="M1503.29 1720.96 L1503.29 1720.96 L1503.57 1720.96 L1503.57 1720.96 L1503.29 1720.96 L1503.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1503.29,1720.96 1503.29,1720.96 1503.57,1720.96 1503.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1503.57 1720.96 L1503.57 1720.96 L1503.85 1720.96 L1503.85 1720.96 L1503.57 1720.96 L1503.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1503.57,1720.96 1503.57,1720.96 1503.85,1720.96 1503.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1503.85 1720.96 L1503.85 1720.96 L1504.13 1720.96 L1504.13 1720.96 L1503.85 1720.96 L1503.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1503.85,1720.96 1503.85,1720.96 1504.13,1720.96 1503.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1504.13 1720.96 L1504.13 1720.96 L1504.41 1720.96 L1504.41 1720.96 L1504.13 1720.96 L1504.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1504.13,1720.96 1504.13,1720.96 1504.41,1720.96 1504.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1504.41 1720.76 L1504.41 1720.96 L1504.69 1720.96 L1504.69 1720.76 L1504.41 1720.76 L1504.41 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1504.41,1720.76 1504.41,1720.96 1504.69,1720.96 1504.69,1720.76 1504.41,1720.76 "/>
<path clip-path="url(#clip322)" d="M1504.69 1720.96 L1504.69 1720.96 L1504.98 1720.96 L1504.98 1720.96 L1504.69 1720.96 L1504.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1504.69,1720.96 1504.69,1720.96 1504.98,1720.96 1504.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1504.98 1720.96 L1504.98 1720.96 L1505.26 1720.96 L1505.26 1720.96 L1504.98 1720.96 L1504.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1504.98,1720.96 1504.98,1720.96 1505.26,1720.96 1504.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1505.26 1720.96 L1505.26 1720.96 L1505.54 1720.96 L1505.54 1720.96 L1505.26 1720.96 L1505.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1505.26,1720.96 1505.26,1720.96 1505.54,1720.96 1505.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1505.54 1720.96 L1505.54 1720.96 L1505.82 1720.96 L1505.82 1720.96 L1505.54 1720.96 L1505.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1505.54,1720.96 1505.54,1720.96 1505.82,1720.96 1505.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1505.82 1720.96 L1505.82 1720.96 L1506.1 1720.96 L1506.1 1720.96 L1505.82 1720.96 L1505.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1505.82,1720.96 1505.82,1720.96 1506.1,1720.96 1505.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1506.1 1720.96 L1506.1 1720.96 L1506.38 1720.96 L1506.38 1720.96 L1506.1 1720.96 L1506.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1506.1,1720.96 1506.1,1720.96 1506.38,1720.96 1506.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1506.38 1720.96 L1506.38 1720.96 L1506.67 1720.96 L1506.67 1720.96 L1506.38 1720.96 L1506.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1506.38,1720.96 1506.38,1720.96 1506.67,1720.96 1506.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1506.67 1720.96 L1506.67 1720.96 L1506.95 1720.96 L1506.95 1720.96 L1506.67 1720.96 L1506.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1506.67,1720.96 1506.67,1720.96 1506.95,1720.96 1506.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1506.95 1720.96 L1506.95 1720.96 L1507.23 1720.96 L1507.23 1720.96 L1506.95 1720.96 L1506.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1506.95,1720.96 1506.95,1720.96 1507.23,1720.96 1506.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1507.23 1720.96 L1507.23 1720.96 L1507.51 1720.96 L1507.51 1720.96 L1507.23 1720.96 L1507.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1507.23,1720.96 1507.23,1720.96 1507.51,1720.96 1507.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1507.51 1720.96 L1507.51 1720.96 L1507.79 1720.96 L1507.79 1720.96 L1507.51 1720.96 L1507.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1507.51,1720.96 1507.51,1720.96 1507.79,1720.96 1507.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1507.79 1720.96 L1507.79 1720.96 L1508.07 1720.96 L1508.07 1720.96 L1507.79 1720.96 L1507.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1507.79,1720.96 1507.79,1720.96 1508.07,1720.96 1507.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1508.07 1720.96 L1508.07 1720.96 L1508.36 1720.96 L1508.36 1720.96 L1508.07 1720.96 L1508.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1508.07,1720.96 1508.07,1720.96 1508.36,1720.96 1508.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1508.36 1720.96 L1508.36 1720.96 L1508.64 1720.96 L1508.64 1720.96 L1508.36 1720.96 L1508.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1508.36,1720.96 1508.36,1720.96 1508.64,1720.96 1508.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1508.64 1720.96 L1508.64 1720.96 L1508.92 1720.96 L1508.92 1720.96 L1508.64 1720.96 L1508.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1508.64,1720.96 1508.64,1720.96 1508.92,1720.96 1508.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1508.92 1720.96 L1508.92 1720.96 L1509.2 1720.96 L1509.2 1720.96 L1508.92 1720.96 L1508.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1508.92,1720.96 1508.92,1720.96 1509.2,1720.96 1508.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1509.2 1720.96 L1509.2 1720.96 L1509.48 1720.96 L1509.48 1720.96 L1509.2 1720.96 L1509.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1509.2,1720.96 1509.2,1720.96 1509.48,1720.96 1509.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1509.48 1720.96 L1509.48 1720.96 L1509.77 1720.96 L1509.77 1720.96 L1509.48 1720.96 L1509.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1509.48,1720.96 1509.48,1720.96 1509.77,1720.96 1509.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1509.77 1720.96 L1509.77 1720.96 L1510.05 1720.96 L1510.05 1720.96 L1509.77 1720.96 L1509.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1509.77,1720.96 1509.77,1720.96 1510.05,1720.96 1509.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1510.05 1720.96 L1510.05 1720.96 L1510.33 1720.96 L1510.33 1720.96 L1510.05 1720.96 L1510.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1510.05,1720.96 1510.05,1720.96 1510.33,1720.96 1510.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1510.33 1720.96 L1510.33 1720.96 L1510.61 1720.96 L1510.61 1720.96 L1510.33 1720.96 L1510.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1510.33,1720.96 1510.33,1720.96 1510.61,1720.96 1510.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1510.61 1720.96 L1510.61 1720.96 L1510.89 1720.96 L1510.89 1720.96 L1510.61 1720.96 L1510.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1510.61,1720.96 1510.61,1720.96 1510.89,1720.96 1510.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1510.89 1720.96 L1510.89 1720.96 L1511.17 1720.96 L1511.17 1720.96 L1510.89 1720.96 L1510.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1510.89,1720.96 1510.89,1720.96 1511.17,1720.96 1510.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1511.17 1720.96 L1511.17 1720.96 L1511.46 1720.96 L1511.46 1720.96 L1511.17 1720.96 L1511.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1511.17,1720.96 1511.17,1720.96 1511.46,1720.96 1511.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1511.46 1720.96 L1511.46 1720.96 L1511.74 1720.96 L1511.74 1720.96 L1511.46 1720.96 L1511.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1511.46,1720.96 1511.46,1720.96 1511.74,1720.96 1511.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1511.74 1720.96 L1511.74 1720.96 L1512.02 1720.96 L1512.02 1720.96 L1511.74 1720.96 L1511.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1511.74,1720.96 1511.74,1720.96 1512.02,1720.96 1511.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1512.02 1720.96 L1512.02 1720.96 L1512.3 1720.96 L1512.3 1720.96 L1512.02 1720.96 L1512.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1512.02,1720.96 1512.02,1720.96 1512.3,1720.96 1512.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1512.3 1720.96 L1512.3 1720.96 L1512.58 1720.96 L1512.58 1720.96 L1512.3 1720.96 L1512.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1512.3,1720.96 1512.3,1720.96 1512.58,1720.96 1512.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1512.58 1720.96 L1512.58 1720.96 L1512.86 1720.96 L1512.86 1720.96 L1512.58 1720.96 L1512.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1512.58,1720.96 1512.58,1720.96 1512.86,1720.96 1512.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1512.86 1720.96 L1512.86 1720.96 L1513.15 1720.96 L1513.15 1720.96 L1512.86 1720.96 L1512.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1512.86,1720.96 1512.86,1720.96 1513.15,1720.96 1512.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1513.15 1720.96 L1513.15 1720.96 L1513.43 1720.96 L1513.43 1720.96 L1513.15 1720.96 L1513.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1513.15,1720.96 1513.15,1720.96 1513.43,1720.96 1513.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1513.43 1720.96 L1513.43 1720.96 L1513.71 1720.96 L1513.71 1720.96 L1513.43 1720.96 L1513.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1513.43,1720.96 1513.43,1720.96 1513.71,1720.96 1513.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1513.71 1720.96 L1513.71 1720.96 L1513.99 1720.96 L1513.99 1720.96 L1513.71 1720.96 L1513.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1513.71,1720.96 1513.71,1720.96 1513.99,1720.96 1513.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1513.99 1720.96 L1513.99 1720.96 L1514.27 1720.96 L1514.27 1720.96 L1513.99 1720.96 L1513.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1513.99,1720.96 1513.99,1720.96 1514.27,1720.96 1513.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1514.27 1720.96 L1514.27 1720.96 L1514.55 1720.96 L1514.55 1720.96 L1514.27 1720.96 L1514.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1514.27,1720.96 1514.27,1720.96 1514.55,1720.96 1514.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1514.55 1720.96 L1514.55 1720.96 L1514.84 1720.96 L1514.84 1720.96 L1514.55 1720.96 L1514.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1514.55,1720.96 1514.55,1720.96 1514.84,1720.96 1514.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1514.84 1720.96 L1514.84 1720.96 L1515.12 1720.96 L1515.12 1720.96 L1514.84 1720.96 L1514.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1514.84,1720.96 1514.84,1720.96 1515.12,1720.96 1514.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1515.12 1720.96 L1515.12 1720.96 L1515.4 1720.96 L1515.4 1720.96 L1515.12 1720.96 L1515.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1515.12,1720.96 1515.12,1720.96 1515.4,1720.96 1515.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1515.4 1720.96 L1515.4 1720.96 L1515.68 1720.96 L1515.68 1720.96 L1515.4 1720.96 L1515.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1515.4,1720.96 1515.4,1720.96 1515.68,1720.96 1515.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1515.68 1720.96 L1515.68 1720.96 L1515.96 1720.96 L1515.96 1720.96 L1515.68 1720.96 L1515.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1515.68,1720.96 1515.68,1720.96 1515.96,1720.96 1515.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1515.96 1720.96 L1515.96 1720.96 L1516.25 1720.96 L1516.25 1720.96 L1515.96 1720.96 L1515.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1515.96,1720.96 1515.96,1720.96 1516.25,1720.96 1515.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1516.25 1720.96 L1516.25 1720.96 L1516.53 1720.96 L1516.53 1720.96 L1516.25 1720.96 L1516.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1516.25,1720.96 1516.25,1720.96 1516.53,1720.96 1516.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1516.53 1720.96 L1516.53 1720.96 L1516.81 1720.96 L1516.81 1720.96 L1516.53 1720.96 L1516.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1516.53,1720.96 1516.53,1720.96 1516.81,1720.96 1516.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1516.81 1720.96 L1516.81 1720.96 L1517.09 1720.96 L1517.09 1720.96 L1516.81 1720.96 L1516.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1516.81,1720.96 1516.81,1720.96 1517.09,1720.96 1516.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1517.09 1720.96 L1517.09 1720.96 L1517.37 1720.96 L1517.37 1720.96 L1517.09 1720.96 L1517.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1517.09,1720.96 1517.09,1720.96 1517.37,1720.96 1517.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1517.37 1720.96 L1517.37 1720.96 L1517.65 1720.96 L1517.65 1720.96 L1517.37 1720.96 L1517.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1517.37,1720.96 1517.37,1720.96 1517.65,1720.96 1517.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1517.65 1720.96 L1517.65 1720.96 L1517.94 1720.96 L1517.94 1720.96 L1517.65 1720.96 L1517.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1517.65,1720.96 1517.65,1720.96 1517.94,1720.96 1517.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1517.94 1720.96 L1517.94 1720.96 L1518.22 1720.96 L1518.22 1720.96 L1517.94 1720.96 L1517.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1517.94,1720.96 1517.94,1720.96 1518.22,1720.96 1517.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1518.22 1720.96 L1518.22 1720.96 L1518.5 1720.96 L1518.5 1720.96 L1518.22 1720.96 L1518.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1518.22,1720.96 1518.22,1720.96 1518.5,1720.96 1518.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1518.5 1720.96 L1518.5 1720.96 L1518.78 1720.96 L1518.78 1720.96 L1518.5 1720.96 L1518.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1518.5,1720.96 1518.5,1720.96 1518.78,1720.96 1518.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1518.78 1720.96 L1518.78 1720.96 L1519.06 1720.96 L1519.06 1720.96 L1518.78 1720.96 L1518.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1518.78,1720.96 1518.78,1720.96 1519.06,1720.96 1518.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1519.06 1720.96 L1519.06 1720.96 L1519.34 1720.96 L1519.34 1720.96 L1519.06 1720.96 L1519.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1519.06,1720.96 1519.06,1720.96 1519.34,1720.96 1519.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1519.34 1720.96 L1519.34 1720.96 L1519.63 1720.96 L1519.63 1720.96 L1519.34 1720.96 L1519.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1519.34,1720.96 1519.34,1720.96 1519.63,1720.96 1519.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1519.63 1720.96 L1519.63 1720.96 L1519.91 1720.96 L1519.91 1720.96 L1519.63 1720.96 L1519.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1519.63,1720.96 1519.63,1720.96 1519.91,1720.96 1519.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1519.91 1720.96 L1519.91 1720.96 L1520.19 1720.96 L1520.19 1720.96 L1519.91 1720.96 L1519.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1519.91,1720.96 1519.91,1720.96 1520.19,1720.96 1519.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1520.19 1720.96 L1520.19 1720.96 L1520.47 1720.96 L1520.47 1720.96 L1520.19 1720.96 L1520.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1520.19,1720.96 1520.19,1720.96 1520.47,1720.96 1520.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1520.47 1720.96 L1520.47 1720.96 L1520.75 1720.96 L1520.75 1720.96 L1520.47 1720.96 L1520.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1520.47,1720.96 1520.47,1720.96 1520.75,1720.96 1520.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1520.75 1720.96 L1520.75 1720.96 L1521.03 1720.96 L1521.03 1720.96 L1520.75 1720.96 L1520.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1520.75,1720.96 1520.75,1720.96 1521.03,1720.96 1520.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1521.03 1720.96 L1521.03 1720.96 L1521.32 1720.96 L1521.32 1720.96 L1521.03 1720.96 L1521.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1521.03,1720.96 1521.03,1720.96 1521.32,1720.96 1521.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1521.32 1720.96 L1521.32 1720.96 L1521.6 1720.96 L1521.6 1720.96 L1521.32 1720.96 L1521.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1521.32,1720.96 1521.32,1720.96 1521.6,1720.96 1521.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1521.6 1720.96 L1521.6 1720.96 L1521.88 1720.96 L1521.88 1720.96 L1521.6 1720.96 L1521.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1521.6,1720.96 1521.6,1720.96 1521.88,1720.96 1521.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1521.88 1720.96 L1521.88 1720.96 L1522.16 1720.96 L1522.16 1720.96 L1521.88 1720.96 L1521.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1521.88,1720.96 1521.88,1720.96 1522.16,1720.96 1521.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1522.16 1720.96 L1522.16 1720.96 L1522.44 1720.96 L1522.44 1720.96 L1522.16 1720.96 L1522.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1522.16,1720.96 1522.16,1720.96 1522.44,1720.96 1522.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1522.44 1720.96 L1522.44 1720.96 L1522.72 1720.96 L1522.72 1720.96 L1522.44 1720.96 L1522.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1522.44,1720.96 1522.44,1720.96 1522.72,1720.96 1522.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1522.72 1720.96 L1522.72 1720.96 L1523.01 1720.96 L1523.01 1720.96 L1522.72 1720.96 L1522.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1522.72,1720.96 1522.72,1720.96 1523.01,1720.96 1522.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1523.01 1720.96 L1523.01 1720.96 L1523.29 1720.96 L1523.29 1720.96 L1523.01 1720.96 L1523.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1523.01,1720.96 1523.01,1720.96 1523.29,1720.96 1523.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1523.29 1720.76 L1523.29 1720.96 L1523.57 1720.96 L1523.57 1720.76 L1523.29 1720.76 L1523.29 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1523.29,1720.76 1523.29,1720.96 1523.57,1720.96 1523.57,1720.76 1523.29,1720.76 "/>
<path clip-path="url(#clip322)" d="M1523.57 1720.96 L1523.57 1720.96 L1523.85 1720.96 L1523.85 1720.96 L1523.57 1720.96 L1523.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1523.57,1720.96 1523.57,1720.96 1523.85,1720.96 1523.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1523.85 1720.96 L1523.85 1720.96 L1524.13 1720.96 L1524.13 1720.96 L1523.85 1720.96 L1523.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1523.85,1720.96 1523.85,1720.96 1524.13,1720.96 1523.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1524.13 1720.96 L1524.13 1720.96 L1524.42 1720.96 L1524.42 1720.96 L1524.13 1720.96 L1524.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1524.13,1720.96 1524.13,1720.96 1524.42,1720.96 1524.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1524.42 1720.96 L1524.42 1720.96 L1524.7 1720.96 L1524.7 1720.96 L1524.42 1720.96 L1524.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1524.42,1720.96 1524.42,1720.96 1524.7,1720.96 1524.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1524.7 1720.96 L1524.7 1720.96 L1524.98 1720.96 L1524.98 1720.96 L1524.7 1720.96 L1524.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1524.7,1720.96 1524.7,1720.96 1524.98,1720.96 1524.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1524.98 1720.96 L1524.98 1720.96 L1525.26 1720.96 L1525.26 1720.96 L1524.98 1720.96 L1524.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1524.98,1720.96 1524.98,1720.96 1525.26,1720.96 1524.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1525.26 1720.96 L1525.26 1720.96 L1525.54 1720.96 L1525.54 1720.96 L1525.26 1720.96 L1525.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1525.26,1720.96 1525.26,1720.96 1525.54,1720.96 1525.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1525.54 1720.76 L1525.54 1720.96 L1525.82 1720.96 L1525.82 1720.76 L1525.54 1720.76 L1525.54 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1525.54,1720.76 1525.54,1720.96 1525.82,1720.96 1525.82,1720.76 1525.54,1720.76 "/>
<path clip-path="url(#clip322)" d="M1525.82 1720.96 L1525.82 1720.96 L1526.11 1720.96 L1526.11 1720.96 L1525.82 1720.96 L1525.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1525.82,1720.96 1525.82,1720.96 1526.11,1720.96 1525.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1526.11 1720.96 L1526.11 1720.96 L1526.39 1720.96 L1526.39 1720.96 L1526.11 1720.96 L1526.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1526.11,1720.96 1526.11,1720.96 1526.39,1720.96 1526.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1526.39 1720.96 L1526.39 1720.96 L1526.67 1720.96 L1526.67 1720.96 L1526.39 1720.96 L1526.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1526.39,1720.96 1526.39,1720.96 1526.67,1720.96 1526.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1526.67 1720.96 L1526.67 1720.96 L1526.95 1720.96 L1526.95 1720.96 L1526.67 1720.96 L1526.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1526.67,1720.96 1526.67,1720.96 1526.95,1720.96 1526.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1526.95 1720.96 L1526.95 1720.96 L1527.23 1720.96 L1527.23 1720.96 L1526.95 1720.96 L1526.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1526.95,1720.96 1526.95,1720.96 1527.23,1720.96 1526.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1527.23 1720.96 L1527.23 1720.96 L1527.51 1720.96 L1527.51 1720.96 L1527.23 1720.96 L1527.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1527.23,1720.96 1527.23,1720.96 1527.51,1720.96 1527.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1527.51 1720.96 L1527.51 1720.96 L1527.8 1720.96 L1527.8 1720.96 L1527.51 1720.96 L1527.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1527.51,1720.96 1527.51,1720.96 1527.8,1720.96 1527.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1527.8 1720.96 L1527.8 1720.96 L1528.08 1720.96 L1528.08 1720.96 L1527.8 1720.96 L1527.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1527.8,1720.96 1527.8,1720.96 1528.08,1720.96 1527.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1528.08 1720.96 L1528.08 1720.96 L1528.36 1720.96 L1528.36 1720.96 L1528.08 1720.96 L1528.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1528.08,1720.96 1528.08,1720.96 1528.36,1720.96 1528.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1528.36 1720.96 L1528.36 1720.96 L1528.64 1720.96 L1528.64 1720.96 L1528.36 1720.96 L1528.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1528.36,1720.96 1528.36,1720.96 1528.64,1720.96 1528.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1528.64 1720.96 L1528.64 1720.96 L1528.92 1720.96 L1528.92 1720.96 L1528.64 1720.96 L1528.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1528.64,1720.96 1528.64,1720.96 1528.92,1720.96 1528.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1528.92 1720.96 L1528.92 1720.96 L1529.2 1720.96 L1529.2 1720.96 L1528.92 1720.96 L1528.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1528.92,1720.96 1528.92,1720.96 1529.2,1720.96 1528.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1529.2 1720.96 L1529.2 1720.96 L1529.49 1720.96 L1529.49 1720.96 L1529.2 1720.96 L1529.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1529.2,1720.96 1529.2,1720.96 1529.49,1720.96 1529.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1529.49 1720.96 L1529.49 1720.96 L1529.77 1720.96 L1529.77 1720.96 L1529.49 1720.96 L1529.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1529.49,1720.96 1529.49,1720.96 1529.77,1720.96 1529.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1529.77 1720.96 L1529.77 1720.96 L1530.05 1720.96 L1530.05 1720.96 L1529.77 1720.96 L1529.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1529.77,1720.96 1529.77,1720.96 1530.05,1720.96 1529.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1530.05 1720.96 L1530.05 1720.96 L1530.33 1720.96 L1530.33 1720.96 L1530.05 1720.96 L1530.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1530.05,1720.96 1530.05,1720.96 1530.33,1720.96 1530.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1530.33 1720.96 L1530.33 1720.96 L1530.61 1720.96 L1530.61 1720.96 L1530.33 1720.96 L1530.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1530.33,1720.96 1530.33,1720.96 1530.61,1720.96 1530.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1530.61 1720.96 L1530.61 1720.96 L1530.89 1720.96 L1530.89 1720.96 L1530.61 1720.96 L1530.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1530.61,1720.96 1530.61,1720.96 1530.89,1720.96 1530.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1530.89 1720.96 L1530.89 1720.96 L1531.18 1720.96 L1531.18 1720.96 L1530.89 1720.96 L1530.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1530.89,1720.96 1530.89,1720.96 1531.18,1720.96 1530.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1531.18 1720.96 L1531.18 1720.96 L1531.46 1720.96 L1531.46 1720.96 L1531.18 1720.96 L1531.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1531.18,1720.96 1531.18,1720.96 1531.46,1720.96 1531.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1531.46 1720.96 L1531.46 1720.96 L1531.74 1720.96 L1531.74 1720.96 L1531.46 1720.96 L1531.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1531.46,1720.96 1531.46,1720.96 1531.74,1720.96 1531.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1531.74 1720.96 L1531.74 1720.96 L1532.02 1720.96 L1532.02 1720.96 L1531.74 1720.96 L1531.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1531.74,1720.96 1531.74,1720.96 1532.02,1720.96 1531.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1532.02 1720.96 L1532.02 1720.96 L1532.3 1720.96 L1532.3 1720.96 L1532.02 1720.96 L1532.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1532.02,1720.96 1532.02,1720.96 1532.3,1720.96 1532.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1532.3 1720.76 L1532.3 1720.96 L1532.59 1720.96 L1532.59 1720.76 L1532.3 1720.76 L1532.3 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1532.3,1720.76 1532.3,1720.96 1532.59,1720.96 1532.59,1720.76 1532.3,1720.76 "/>
<path clip-path="url(#clip322)" d="M1532.59 1720.96 L1532.59 1720.96 L1532.87 1720.96 L1532.87 1720.96 L1532.59 1720.96 L1532.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1532.59,1720.96 1532.59,1720.96 1532.87,1720.96 1532.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1532.87 1720.96 L1532.87 1720.96 L1533.15 1720.96 L1533.15 1720.96 L1532.87 1720.96 L1532.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1532.87,1720.96 1532.87,1720.96 1533.15,1720.96 1532.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1533.15 1720.96 L1533.15 1720.96 L1533.43 1720.96 L1533.43 1720.96 L1533.15 1720.96 L1533.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1533.15,1720.96 1533.15,1720.96 1533.43,1720.96 1533.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1533.43 1720.96 L1533.43 1720.96 L1533.71 1720.96 L1533.71 1720.96 L1533.43 1720.96 L1533.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1533.43,1720.96 1533.43,1720.96 1533.71,1720.96 1533.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1533.71 1720.96 L1533.71 1720.96 L1533.99 1720.96 L1533.99 1720.96 L1533.71 1720.96 L1533.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1533.71,1720.96 1533.71,1720.96 1533.99,1720.96 1533.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1533.99 1720.96 L1533.99 1720.96 L1534.28 1720.96 L1534.28 1720.96 L1533.99 1720.96 L1533.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1533.99,1720.96 1533.99,1720.96 1534.28,1720.96 1533.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1534.28 1720.96 L1534.28 1720.96 L1534.56 1720.96 L1534.56 1720.96 L1534.28 1720.96 L1534.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1534.28,1720.96 1534.28,1720.96 1534.56,1720.96 1534.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1534.56 1720.96 L1534.56 1720.96 L1534.84 1720.96 L1534.84 1720.96 L1534.56 1720.96 L1534.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1534.56,1720.96 1534.56,1720.96 1534.84,1720.96 1534.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1534.84 1720.96 L1534.84 1720.96 L1535.12 1720.96 L1535.12 1720.96 L1534.84 1720.96 L1534.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1534.84,1720.96 1534.84,1720.96 1535.12,1720.96 1534.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1535.12 1720.96 L1535.12 1720.96 L1535.4 1720.96 L1535.4 1720.96 L1535.12 1720.96 L1535.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1535.12,1720.96 1535.12,1720.96 1535.4,1720.96 1535.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1535.4 1720.96 L1535.4 1720.96 L1535.68 1720.96 L1535.68 1720.96 L1535.4 1720.96 L1535.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1535.4,1720.96 1535.4,1720.96 1535.68,1720.96 1535.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1535.68 1720.96 L1535.68 1720.96 L1535.97 1720.96 L1535.97 1720.96 L1535.68 1720.96 L1535.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1535.68,1720.96 1535.68,1720.96 1535.97,1720.96 1535.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1535.97 1720.96 L1535.97 1720.96 L1536.25 1720.96 L1536.25 1720.96 L1535.97 1720.96 L1535.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1535.97,1720.96 1535.97,1720.96 1536.25,1720.96 1535.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1536.25 1720.96 L1536.25 1720.96 L1536.53 1720.96 L1536.53 1720.96 L1536.25 1720.96 L1536.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1536.25,1720.96 1536.25,1720.96 1536.53,1720.96 1536.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1536.53 1720.96 L1536.53 1720.96 L1536.81 1720.96 L1536.81 1720.96 L1536.53 1720.96 L1536.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1536.53,1720.96 1536.53,1720.96 1536.81,1720.96 1536.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1536.81 1720.96 L1536.81 1720.96 L1537.09 1720.96 L1537.09 1720.96 L1536.81 1720.96 L1536.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1536.81,1720.96 1536.81,1720.96 1537.09,1720.96 1536.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1537.09 1720.96 L1537.09 1720.96 L1537.37 1720.96 L1537.37 1720.96 L1537.09 1720.96 L1537.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1537.09,1720.96 1537.09,1720.96 1537.37,1720.96 1537.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1537.37 1720.96 L1537.37 1720.96 L1537.66 1720.96 L1537.66 1720.96 L1537.37 1720.96 L1537.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1537.37,1720.96 1537.37,1720.96 1537.66,1720.96 1537.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1537.66 1720.96 L1537.66 1720.96 L1537.94 1720.96 L1537.94 1720.96 L1537.66 1720.96 L1537.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1537.66,1720.96 1537.66,1720.96 1537.94,1720.96 1537.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1537.94 1720.96 L1537.94 1720.96 L1538.22 1720.96 L1538.22 1720.96 L1537.94 1720.96 L1537.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1537.94,1720.96 1537.94,1720.96 1538.22,1720.96 1537.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1538.22 1720.96 L1538.22 1720.96 L1538.5 1720.96 L1538.5 1720.96 L1538.22 1720.96 L1538.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1538.22,1720.96 1538.22,1720.96 1538.5,1720.96 1538.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1538.5 1720.96 L1538.5 1720.96 L1538.78 1720.96 L1538.78 1720.96 L1538.5 1720.96 L1538.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1538.5,1720.96 1538.5,1720.96 1538.78,1720.96 1538.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1538.78 1720.96 L1538.78 1720.96 L1539.06 1720.96 L1539.06 1720.96 L1538.78 1720.96 L1538.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1538.78,1720.96 1538.78,1720.96 1539.06,1720.96 1538.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1539.06 1720.96 L1539.06 1720.96 L1539.35 1720.96 L1539.35 1720.96 L1539.06 1720.96 L1539.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1539.06,1720.96 1539.06,1720.96 1539.35,1720.96 1539.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1539.35 1720.96 L1539.35 1720.96 L1539.63 1720.96 L1539.63 1720.96 L1539.35 1720.96 L1539.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1539.35,1720.96 1539.35,1720.96 1539.63,1720.96 1539.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1539.63 1720.96 L1539.63 1720.96 L1539.91 1720.96 L1539.91 1720.96 L1539.63 1720.96 L1539.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1539.63,1720.96 1539.63,1720.96 1539.91,1720.96 1539.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1539.91 1720.96 L1539.91 1720.96 L1540.19 1720.96 L1540.19 1720.96 L1539.91 1720.96 L1539.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1539.91,1720.96 1539.91,1720.96 1540.19,1720.96 1539.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1540.19 1720.96 L1540.19 1720.96 L1540.47 1720.96 L1540.47 1720.96 L1540.19 1720.96 L1540.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1540.19,1720.96 1540.19,1720.96 1540.47,1720.96 1540.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1540.47 1720.96 L1540.47 1720.96 L1540.76 1720.96 L1540.76 1720.96 L1540.47 1720.96 L1540.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1540.47,1720.96 1540.47,1720.96 1540.76,1720.96 1540.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1540.76 1720.96 L1540.76 1720.96 L1541.04 1720.96 L1541.04 1720.96 L1540.76 1720.96 L1540.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1540.76,1720.96 1540.76,1720.96 1541.04,1720.96 1540.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1541.04 1720.96 L1541.04 1720.96 L1541.32 1720.96 L1541.32 1720.96 L1541.04 1720.96 L1541.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1541.04,1720.96 1541.04,1720.96 1541.32,1720.96 1541.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1541.32 1720.96 L1541.32 1720.96 L1541.6 1720.96 L1541.6 1720.96 L1541.32 1720.96 L1541.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1541.32,1720.96 1541.32,1720.96 1541.6,1720.96 1541.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1541.6 1720.96 L1541.6 1720.96 L1541.88 1720.96 L1541.88 1720.96 L1541.6 1720.96 L1541.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1541.6,1720.96 1541.6,1720.96 1541.88,1720.96 1541.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1541.88 1720.96 L1541.88 1720.96 L1542.16 1720.96 L1542.16 1720.96 L1541.88 1720.96 L1541.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1541.88,1720.96 1541.88,1720.96 1542.16,1720.96 1541.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1542.16 1720.96 L1542.16 1720.96 L1542.45 1720.96 L1542.45 1720.96 L1542.16 1720.96 L1542.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1542.16,1720.96 1542.16,1720.96 1542.45,1720.96 1542.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1542.45 1720.96 L1542.45 1720.96 L1542.73 1720.96 L1542.73 1720.96 L1542.45 1720.96 L1542.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1542.45,1720.96 1542.45,1720.96 1542.73,1720.96 1542.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1542.73 1720.96 L1542.73 1720.96 L1543.01 1720.96 L1543.01 1720.96 L1542.73 1720.96 L1542.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1542.73,1720.96 1542.73,1720.96 1543.01,1720.96 1542.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1543.01 1720.96 L1543.01 1720.96 L1543.29 1720.96 L1543.29 1720.96 L1543.01 1720.96 L1543.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1543.01,1720.96 1543.01,1720.96 1543.29,1720.96 1543.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1543.29 1720.96 L1543.29 1720.96 L1543.57 1720.96 L1543.57 1720.96 L1543.29 1720.96 L1543.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1543.29,1720.96 1543.29,1720.96 1543.57,1720.96 1543.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1543.57 1720.96 L1543.57 1720.96 L1543.85 1720.96 L1543.85 1720.96 L1543.57 1720.96 L1543.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1543.57,1720.96 1543.57,1720.96 1543.85,1720.96 1543.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1543.85 1720.96 L1543.85 1720.96 L1544.14 1720.96 L1544.14 1720.96 L1543.85 1720.96 L1543.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1543.85,1720.96 1543.85,1720.96 1544.14,1720.96 1543.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1544.14 1720.96 L1544.14 1720.96 L1544.42 1720.96 L1544.42 1720.96 L1544.14 1720.96 L1544.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1544.14,1720.96 1544.14,1720.96 1544.42,1720.96 1544.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1544.42 1720.96 L1544.42 1720.96 L1544.7 1720.96 L1544.7 1720.96 L1544.42 1720.96 L1544.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1544.42,1720.96 1544.42,1720.96 1544.7,1720.96 1544.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1544.7 1720.96 L1544.7 1720.96 L1544.98 1720.96 L1544.98 1720.96 L1544.7 1720.96 L1544.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1544.7,1720.96 1544.7,1720.96 1544.98,1720.96 1544.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1544.98 1720.96 L1544.98 1720.96 L1545.26 1720.96 L1545.26 1720.96 L1544.98 1720.96 L1544.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1544.98,1720.96 1544.98,1720.96 1545.26,1720.96 1544.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1545.26 1720.96 L1545.26 1720.96 L1545.54 1720.96 L1545.54 1720.96 L1545.26 1720.96 L1545.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1545.26,1720.96 1545.26,1720.96 1545.54,1720.96 1545.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1545.54 1720.96 L1545.54 1720.96 L1545.83 1720.96 L1545.83 1720.96 L1545.54 1720.96 L1545.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1545.54,1720.96 1545.54,1720.96 1545.83,1720.96 1545.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1545.83 1720.96 L1545.83 1720.96 L1546.11 1720.96 L1546.11 1720.96 L1545.83 1720.96 L1545.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1545.83,1720.96 1545.83,1720.96 1546.11,1720.96 1545.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1546.11 1720.96 L1546.11 1720.96 L1546.39 1720.96 L1546.39 1720.96 L1546.11 1720.96 L1546.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1546.11,1720.96 1546.11,1720.96 1546.39,1720.96 1546.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1546.39 1720.96 L1546.39 1720.96 L1546.67 1720.96 L1546.67 1720.96 L1546.39 1720.96 L1546.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1546.39,1720.96 1546.39,1720.96 1546.67,1720.96 1546.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1546.67 1720.96 L1546.67 1720.96 L1546.95 1720.96 L1546.95 1720.96 L1546.67 1720.96 L1546.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1546.67,1720.96 1546.67,1720.96 1546.95,1720.96 1546.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1546.95 1720.96 L1546.95 1720.96 L1547.23 1720.96 L1547.23 1720.96 L1546.95 1720.96 L1546.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1546.95,1720.96 1546.95,1720.96 1547.23,1720.96 1546.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1547.23 1720.96 L1547.23 1720.96 L1547.52 1720.96 L1547.52 1720.96 L1547.23 1720.96 L1547.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1547.23,1720.96 1547.23,1720.96 1547.52,1720.96 1547.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1547.52 1720.96 L1547.52 1720.96 L1547.8 1720.96 L1547.8 1720.96 L1547.52 1720.96 L1547.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1547.52,1720.96 1547.52,1720.96 1547.8,1720.96 1547.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1547.8 1720.96 L1547.8 1720.96 L1548.08 1720.96 L1548.08 1720.96 L1547.8 1720.96 L1547.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1547.8,1720.96 1547.8,1720.96 1548.08,1720.96 1547.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1548.08 1720.96 L1548.08 1720.96 L1548.36 1720.96 L1548.36 1720.96 L1548.08 1720.96 L1548.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1548.08,1720.96 1548.08,1720.96 1548.36,1720.96 1548.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1548.36 1720.96 L1548.36 1720.96 L1548.64 1720.96 L1548.64 1720.96 L1548.36 1720.96 L1548.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1548.36,1720.96 1548.36,1720.96 1548.64,1720.96 1548.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1548.64 1720.76 L1548.64 1720.96 L1548.93 1720.96 L1548.93 1720.76 L1548.64 1720.76 L1548.64 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1548.64,1720.76 1548.64,1720.96 1548.93,1720.96 1548.93,1720.76 1548.64,1720.76 "/>
<path clip-path="url(#clip322)" d="M1548.93 1720.96 L1548.93 1720.96 L1549.21 1720.96 L1549.21 1720.96 L1548.93 1720.96 L1548.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1548.93,1720.96 1548.93,1720.96 1549.21,1720.96 1548.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1549.21 1720.96 L1549.21 1720.96 L1549.49 1720.96 L1549.49 1720.96 L1549.21 1720.96 L1549.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1549.21,1720.96 1549.21,1720.96 1549.49,1720.96 1549.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1549.49 1720.96 L1549.49 1720.96 L1549.77 1720.96 L1549.77 1720.96 L1549.49 1720.96 L1549.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1549.49,1720.96 1549.49,1720.96 1549.77,1720.96 1549.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1549.77 1720.96 L1549.77 1720.96 L1550.05 1720.96 L1550.05 1720.96 L1549.77 1720.96 L1549.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1549.77,1720.96 1549.77,1720.96 1550.05,1720.96 1549.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1550.05 1720.96 L1550.05 1720.96 L1550.33 1720.96 L1550.33 1720.96 L1550.05 1720.96 L1550.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1550.05,1720.96 1550.05,1720.96 1550.33,1720.96 1550.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1550.33 1720.96 L1550.33 1720.96 L1550.62 1720.96 L1550.62 1720.96 L1550.33 1720.96 L1550.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1550.33,1720.96 1550.33,1720.96 1550.62,1720.96 1550.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1550.62 1720.96 L1550.62 1720.96 L1550.9 1720.96 L1550.9 1720.96 L1550.62 1720.96 L1550.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1550.62,1720.96 1550.62,1720.96 1550.9,1720.96 1550.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1550.9 1720.96 L1550.9 1720.96 L1551.18 1720.96 L1551.18 1720.96 L1550.9 1720.96 L1550.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1550.9,1720.96 1550.9,1720.96 1551.18,1720.96 1550.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1551.18 1720.96 L1551.18 1720.96 L1551.46 1720.96 L1551.46 1720.96 L1551.18 1720.96 L1551.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1551.18,1720.96 1551.18,1720.96 1551.46,1720.96 1551.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1551.46 1720.96 L1551.46 1720.96 L1551.74 1720.96 L1551.74 1720.96 L1551.46 1720.96 L1551.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1551.46,1720.96 1551.46,1720.96 1551.74,1720.96 1551.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1551.74 1720.96 L1551.74 1720.96 L1552.02 1720.96 L1552.02 1720.96 L1551.74 1720.96 L1551.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1551.74,1720.96 1551.74,1720.96 1552.02,1720.96 1551.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1552.02 1720.96 L1552.02 1720.96 L1552.31 1720.96 L1552.31 1720.96 L1552.02 1720.96 L1552.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1552.02,1720.96 1552.02,1720.96 1552.31,1720.96 1552.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1552.31 1720.96 L1552.31 1720.96 L1552.59 1720.96 L1552.59 1720.96 L1552.31 1720.96 L1552.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1552.31,1720.96 1552.31,1720.96 1552.59,1720.96 1552.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1552.59 1720.96 L1552.59 1720.96 L1552.87 1720.96 L1552.87 1720.96 L1552.59 1720.96 L1552.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1552.59,1720.96 1552.59,1720.96 1552.87,1720.96 1552.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1552.87 1720.96 L1552.87 1720.96 L1553.15 1720.96 L1553.15 1720.96 L1552.87 1720.96 L1552.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1552.87,1720.96 1552.87,1720.96 1553.15,1720.96 1552.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1553.15 1720.96 L1553.15 1720.96 L1553.43 1720.96 L1553.43 1720.96 L1553.15 1720.96 L1553.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1553.15,1720.96 1553.15,1720.96 1553.43,1720.96 1553.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1553.43 1720.96 L1553.43 1720.96 L1553.71 1720.96 L1553.71 1720.96 L1553.43 1720.96 L1553.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1553.43,1720.96 1553.43,1720.96 1553.71,1720.96 1553.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1553.71 1720.96 L1553.71 1720.96 L1554 1720.96 L1554 1720.96 L1553.71 1720.96 L1553.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1553.71,1720.96 1553.71,1720.96 1554,1720.96 1553.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1554 1720.96 L1554 1720.96 L1554.28 1720.96 L1554.28 1720.96 L1554 1720.96 L1554 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1554,1720.96 1554,1720.96 1554.28,1720.96 1554,1720.96 "/>
<path clip-path="url(#clip322)" d="M1554.28 1720.96 L1554.28 1720.96 L1554.56 1720.96 L1554.56 1720.96 L1554.28 1720.96 L1554.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1554.28,1720.96 1554.28,1720.96 1554.56,1720.96 1554.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1554.56 1720.96 L1554.56 1720.96 L1554.84 1720.96 L1554.84 1720.96 L1554.56 1720.96 L1554.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1554.56,1720.96 1554.56,1720.96 1554.84,1720.96 1554.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1554.84 1720.96 L1554.84 1720.96 L1555.12 1720.96 L1555.12 1720.96 L1554.84 1720.96 L1554.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1554.84,1720.96 1554.84,1720.96 1555.12,1720.96 1554.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1555.12 1720.96 L1555.12 1720.96 L1555.4 1720.96 L1555.4 1720.96 L1555.12 1720.96 L1555.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1555.12,1720.96 1555.12,1720.96 1555.4,1720.96 1555.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1555.4 1720.96 L1555.4 1720.96 L1555.69 1720.96 L1555.69 1720.96 L1555.4 1720.96 L1555.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1555.4,1720.96 1555.4,1720.96 1555.69,1720.96 1555.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1555.69 1720.96 L1555.69 1720.96 L1555.97 1720.96 L1555.97 1720.96 L1555.69 1720.96 L1555.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1555.69,1720.96 1555.69,1720.96 1555.97,1720.96 1555.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1555.97 1720.96 L1555.97 1720.96 L1556.25 1720.96 L1556.25 1720.96 L1555.97 1720.96 L1555.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1555.97,1720.96 1555.97,1720.96 1556.25,1720.96 1555.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1556.25 1720.96 L1556.25 1720.96 L1556.53 1720.96 L1556.53 1720.96 L1556.25 1720.96 L1556.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1556.25,1720.96 1556.25,1720.96 1556.53,1720.96 1556.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1556.53 1720.96 L1556.53 1720.96 L1556.81 1720.96 L1556.81 1720.96 L1556.53 1720.96 L1556.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1556.53,1720.96 1556.53,1720.96 1556.81,1720.96 1556.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1556.81 1720.96 L1556.81 1720.96 L1557.1 1720.96 L1557.1 1720.96 L1556.81 1720.96 L1556.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1556.81,1720.96 1556.81,1720.96 1557.1,1720.96 1556.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1557.1 1720.96 L1557.1 1720.96 L1557.38 1720.96 L1557.38 1720.96 L1557.1 1720.96 L1557.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1557.1,1720.96 1557.1,1720.96 1557.38,1720.96 1557.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1557.38 1720.96 L1557.38 1720.96 L1557.66 1720.96 L1557.66 1720.96 L1557.38 1720.96 L1557.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1557.38,1720.96 1557.38,1720.96 1557.66,1720.96 1557.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1557.66 1720.96 L1557.66 1720.96 L1557.94 1720.96 L1557.94 1720.96 L1557.66 1720.96 L1557.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1557.66,1720.96 1557.66,1720.96 1557.94,1720.96 1557.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1557.94 1720.96 L1557.94 1720.96 L1558.22 1720.96 L1558.22 1720.96 L1557.94 1720.96 L1557.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1557.94,1720.96 1557.94,1720.96 1558.22,1720.96 1557.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1558.22 1720.96 L1558.22 1720.96 L1558.5 1720.96 L1558.5 1720.96 L1558.22 1720.96 L1558.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1558.22,1720.96 1558.22,1720.96 1558.5,1720.96 1558.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1558.5 1720.96 L1558.5 1720.96 L1558.79 1720.96 L1558.79 1720.96 L1558.5 1720.96 L1558.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1558.5,1720.96 1558.5,1720.96 1558.79,1720.96 1558.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1558.79 1720.96 L1558.79 1720.96 L1559.07 1720.96 L1559.07 1720.96 L1558.79 1720.96 L1558.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1558.79,1720.96 1558.79,1720.96 1559.07,1720.96 1558.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1559.07 1720.96 L1559.07 1720.96 L1559.35 1720.96 L1559.35 1720.96 L1559.07 1720.96 L1559.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1559.07,1720.96 1559.07,1720.96 1559.35,1720.96 1559.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1559.35 1720.96 L1559.35 1720.96 L1559.63 1720.96 L1559.63 1720.96 L1559.35 1720.96 L1559.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1559.35,1720.96 1559.35,1720.96 1559.63,1720.96 1559.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1559.63 1720.96 L1559.63 1720.96 L1559.91 1720.96 L1559.91 1720.96 L1559.63 1720.96 L1559.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1559.63,1720.96 1559.63,1720.96 1559.91,1720.96 1559.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1559.91 1720.96 L1559.91 1720.96 L1560.19 1720.96 L1560.19 1720.96 L1559.91 1720.96 L1559.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1559.91,1720.96 1559.91,1720.96 1560.19,1720.96 1559.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1560.19 1720.96 L1560.19 1720.96 L1560.48 1720.96 L1560.48 1720.96 L1560.19 1720.96 L1560.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1560.19,1720.96 1560.19,1720.96 1560.48,1720.96 1560.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1560.48 1720.96 L1560.48 1720.96 L1560.76 1720.96 L1560.76 1720.96 L1560.48 1720.96 L1560.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1560.48,1720.96 1560.48,1720.96 1560.76,1720.96 1560.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1560.76 1720.96 L1560.76 1720.96 L1561.04 1720.96 L1561.04 1720.96 L1560.76 1720.96 L1560.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1560.76,1720.96 1560.76,1720.96 1561.04,1720.96 1560.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1561.04 1720.96 L1561.04 1720.96 L1561.32 1720.96 L1561.32 1720.96 L1561.04 1720.96 L1561.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1561.04,1720.96 1561.04,1720.96 1561.32,1720.96 1561.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1561.32 1720.96 L1561.32 1720.96 L1561.6 1720.96 L1561.6 1720.96 L1561.32 1720.96 L1561.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1561.32,1720.96 1561.32,1720.96 1561.6,1720.96 1561.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1561.6 1720.96 L1561.6 1720.96 L1561.88 1720.96 L1561.88 1720.96 L1561.6 1720.96 L1561.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1561.6,1720.96 1561.6,1720.96 1561.88,1720.96 1561.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1561.88 1720.96 L1561.88 1720.96 L1562.17 1720.96 L1562.17 1720.96 L1561.88 1720.96 L1561.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1561.88,1720.96 1561.88,1720.96 1562.17,1720.96 1561.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1562.17 1720.96 L1562.17 1720.96 L1562.45 1720.96 L1562.45 1720.96 L1562.17 1720.96 L1562.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1562.17,1720.96 1562.17,1720.96 1562.45,1720.96 1562.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1562.45 1720.96 L1562.45 1720.96 L1562.73 1720.96 L1562.73 1720.96 L1562.45 1720.96 L1562.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1562.45,1720.96 1562.45,1720.96 1562.73,1720.96 1562.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1562.73 1720.96 L1562.73 1720.96 L1563.01 1720.96 L1563.01 1720.96 L1562.73 1720.96 L1562.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1562.73,1720.96 1562.73,1720.96 1563.01,1720.96 1562.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1563.01 1720.96 L1563.01 1720.96 L1563.29 1720.96 L1563.29 1720.96 L1563.01 1720.96 L1563.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1563.01,1720.96 1563.01,1720.96 1563.29,1720.96 1563.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1563.29 1720.96 L1563.29 1720.96 L1563.57 1720.96 L1563.57 1720.96 L1563.29 1720.96 L1563.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1563.29,1720.96 1563.29,1720.96 1563.57,1720.96 1563.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1563.57 1720.96 L1563.57 1720.96 L1563.86 1720.96 L1563.86 1720.96 L1563.57 1720.96 L1563.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1563.57,1720.96 1563.57,1720.96 1563.86,1720.96 1563.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1563.86 1720.96 L1563.86 1720.96 L1564.14 1720.96 L1564.14 1720.96 L1563.86 1720.96 L1563.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1563.86,1720.96 1563.86,1720.96 1564.14,1720.96 1563.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1564.14 1720.96 L1564.14 1720.96 L1564.42 1720.96 L1564.42 1720.96 L1564.14 1720.96 L1564.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1564.14,1720.96 1564.14,1720.96 1564.42,1720.96 1564.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1564.42 1720.96 L1564.42 1720.96 L1564.7 1720.96 L1564.7 1720.96 L1564.42 1720.96 L1564.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1564.42,1720.96 1564.42,1720.96 1564.7,1720.96 1564.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1564.7 1720.96 L1564.7 1720.96 L1564.98 1720.96 L1564.98 1720.96 L1564.7 1720.96 L1564.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1564.7,1720.96 1564.7,1720.96 1564.98,1720.96 1564.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1564.98 1720.96 L1564.98 1720.96 L1565.27 1720.96 L1565.27 1720.96 L1564.98 1720.96 L1564.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1564.98,1720.96 1564.98,1720.96 1565.27,1720.96 1564.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1565.27 1720.96 L1565.27 1720.96 L1565.55 1720.96 L1565.55 1720.96 L1565.27 1720.96 L1565.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1565.27,1720.96 1565.27,1720.96 1565.55,1720.96 1565.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1565.55 1720.96 L1565.55 1720.96 L1565.83 1720.96 L1565.83 1720.96 L1565.55 1720.96 L1565.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1565.55,1720.96 1565.55,1720.96 1565.83,1720.96 1565.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1565.83 1720.96 L1565.83 1720.96 L1566.11 1720.96 L1566.11 1720.96 L1565.83 1720.96 L1565.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1565.83,1720.96 1565.83,1720.96 1566.11,1720.96 1565.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1566.11 1720.96 L1566.11 1720.96 L1566.39 1720.96 L1566.39 1720.96 L1566.11 1720.96 L1566.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1566.11,1720.96 1566.11,1720.96 1566.39,1720.96 1566.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1566.39 1720.96 L1566.39 1720.96 L1566.67 1720.96 L1566.67 1720.96 L1566.39 1720.96 L1566.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1566.39,1720.96 1566.39,1720.96 1566.67,1720.96 1566.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1566.67 1720.96 L1566.67 1720.96 L1566.96 1720.96 L1566.96 1720.96 L1566.67 1720.96 L1566.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1566.67,1720.96 1566.67,1720.96 1566.96,1720.96 1566.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1566.96 1720.96 L1566.96 1720.96 L1567.24 1720.96 L1567.24 1720.96 L1566.96 1720.96 L1566.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1566.96,1720.96 1566.96,1720.96 1567.24,1720.96 1566.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1567.24 1720.96 L1567.24 1720.96 L1567.52 1720.96 L1567.52 1720.96 L1567.24 1720.96 L1567.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1567.24,1720.96 1567.24,1720.96 1567.52,1720.96 1567.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1567.52 1720.96 L1567.52 1720.96 L1567.8 1720.96 L1567.8 1720.96 L1567.52 1720.96 L1567.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1567.52,1720.96 1567.52,1720.96 1567.8,1720.96 1567.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1567.8 1720.96 L1567.8 1720.96 L1568.08 1720.96 L1568.08 1720.96 L1567.8 1720.96 L1567.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1567.8,1720.96 1567.8,1720.96 1568.08,1720.96 1567.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1568.08 1720.96 L1568.08 1720.96 L1568.36 1720.96 L1568.36 1720.96 L1568.08 1720.96 L1568.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1568.08,1720.96 1568.08,1720.96 1568.36,1720.96 1568.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1568.36 1720.96 L1568.36 1720.96 L1568.65 1720.96 L1568.65 1720.96 L1568.36 1720.96 L1568.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1568.36,1720.96 1568.36,1720.96 1568.65,1720.96 1568.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1568.65 1720.76 L1568.65 1720.96 L1568.93 1720.96 L1568.93 1720.76 L1568.65 1720.76 L1568.65 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1568.65,1720.76 1568.65,1720.96 1568.93,1720.96 1568.93,1720.76 1568.65,1720.76 "/>
<path clip-path="url(#clip322)" d="M1568.93 1720.96 L1568.93 1720.96 L1569.21 1720.96 L1569.21 1720.96 L1568.93 1720.96 L1568.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1568.93,1720.96 1568.93,1720.96 1569.21,1720.96 1568.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1569.21 1720.96 L1569.21 1720.96 L1569.49 1720.96 L1569.49 1720.96 L1569.21 1720.96 L1569.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1569.21,1720.96 1569.21,1720.96 1569.49,1720.96 1569.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1569.49 1720.96 L1569.49 1720.96 L1569.77 1720.96 L1569.77 1720.96 L1569.49 1720.96 L1569.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1569.49,1720.96 1569.49,1720.96 1569.77,1720.96 1569.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1569.77 1720.96 L1569.77 1720.96 L1570.05 1720.96 L1570.05 1720.96 L1569.77 1720.96 L1569.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1569.77,1720.96 1569.77,1720.96 1570.05,1720.96 1569.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1570.05 1720.96 L1570.05 1720.96 L1570.34 1720.96 L1570.34 1720.96 L1570.05 1720.96 L1570.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1570.05,1720.96 1570.05,1720.96 1570.34,1720.96 1570.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1570.34 1720.96 L1570.34 1720.96 L1570.62 1720.96 L1570.62 1720.96 L1570.34 1720.96 L1570.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1570.34,1720.96 1570.34,1720.96 1570.62,1720.96 1570.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1570.62 1720.96 L1570.62 1720.96 L1570.9 1720.96 L1570.9 1720.96 L1570.62 1720.96 L1570.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1570.62,1720.96 1570.62,1720.96 1570.9,1720.96 1570.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1570.9 1720.96 L1570.9 1720.96 L1571.18 1720.96 L1571.18 1720.96 L1570.9 1720.96 L1570.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1570.9,1720.96 1570.9,1720.96 1571.18,1720.96 1570.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1571.18 1720.96 L1571.18 1720.96 L1571.46 1720.96 L1571.46 1720.96 L1571.18 1720.96 L1571.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1571.18,1720.96 1571.18,1720.96 1571.46,1720.96 1571.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1571.46 1720.96 L1571.46 1720.96 L1571.74 1720.96 L1571.74 1720.96 L1571.46 1720.96 L1571.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1571.46,1720.96 1571.46,1720.96 1571.74,1720.96 1571.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1571.74 1720.96 L1571.74 1720.96 L1572.03 1720.96 L1572.03 1720.96 L1571.74 1720.96 L1571.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1571.74,1720.96 1571.74,1720.96 1572.03,1720.96 1571.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1572.03 1720.96 L1572.03 1720.96 L1572.31 1720.96 L1572.31 1720.96 L1572.03 1720.96 L1572.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1572.03,1720.96 1572.03,1720.96 1572.31,1720.96 1572.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1572.31 1720.96 L1572.31 1720.96 L1572.59 1720.96 L1572.59 1720.96 L1572.31 1720.96 L1572.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1572.31,1720.96 1572.31,1720.96 1572.59,1720.96 1572.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1572.59 1720.96 L1572.59 1720.96 L1572.87 1720.96 L1572.87 1720.96 L1572.59 1720.96 L1572.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1572.59,1720.96 1572.59,1720.96 1572.87,1720.96 1572.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1572.87 1720.96 L1572.87 1720.96 L1573.15 1720.96 L1573.15 1720.96 L1572.87 1720.96 L1572.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1572.87,1720.96 1572.87,1720.96 1573.15,1720.96 1572.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1573.15 1720.96 L1573.15 1720.96 L1573.44 1720.96 L1573.44 1720.96 L1573.15 1720.96 L1573.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1573.15,1720.96 1573.15,1720.96 1573.44,1720.96 1573.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1573.44 1720.96 L1573.44 1720.96 L1573.72 1720.96 L1573.72 1720.96 L1573.44 1720.96 L1573.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1573.44,1720.96 1573.44,1720.96 1573.72,1720.96 1573.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1573.72 1720.96 L1573.72 1720.96 L1574 1720.96 L1574 1720.96 L1573.72 1720.96 L1573.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1573.72,1720.96 1573.72,1720.96 1574,1720.96 1573.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1574 1720.96 L1574 1720.96 L1574.28 1720.96 L1574.28 1720.96 L1574 1720.96 L1574 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1574,1720.96 1574,1720.96 1574.28,1720.96 1574,1720.96 "/>
<path clip-path="url(#clip322)" d="M1574.28 1720.96 L1574.28 1720.96 L1574.56 1720.96 L1574.56 1720.96 L1574.28 1720.96 L1574.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1574.28,1720.96 1574.28,1720.96 1574.56,1720.96 1574.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1574.56 1720.96 L1574.56 1720.96 L1574.84 1720.96 L1574.84 1720.96 L1574.56 1720.96 L1574.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1574.56,1720.96 1574.56,1720.96 1574.84,1720.96 1574.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1574.84 1720.96 L1574.84 1720.96 L1575.13 1720.96 L1575.13 1720.96 L1574.84 1720.96 L1574.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1574.84,1720.96 1574.84,1720.96 1575.13,1720.96 1574.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1575.13 1720.96 L1575.13 1720.96 L1575.41 1720.96 L1575.41 1720.96 L1575.13 1720.96 L1575.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1575.13,1720.96 1575.13,1720.96 1575.41,1720.96 1575.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1575.41 1720.96 L1575.41 1720.96 L1575.69 1720.96 L1575.69 1720.96 L1575.41 1720.96 L1575.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1575.41,1720.96 1575.41,1720.96 1575.69,1720.96 1575.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1575.69 1720.96 L1575.69 1720.96 L1575.97 1720.96 L1575.97 1720.96 L1575.69 1720.96 L1575.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1575.69,1720.96 1575.69,1720.96 1575.97,1720.96 1575.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1575.97 1720.96 L1575.97 1720.96 L1576.25 1720.96 L1576.25 1720.96 L1575.97 1720.96 L1575.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1575.97,1720.96 1575.97,1720.96 1576.25,1720.96 1575.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1576.25 1720.96 L1576.25 1720.96 L1576.53 1720.96 L1576.53 1720.96 L1576.25 1720.96 L1576.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1576.25,1720.96 1576.25,1720.96 1576.53,1720.96 1576.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1576.53 1720.96 L1576.53 1720.96 L1576.82 1720.96 L1576.82 1720.96 L1576.53 1720.96 L1576.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1576.53,1720.96 1576.53,1720.96 1576.82,1720.96 1576.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1576.82 1720.96 L1576.82 1720.96 L1577.1 1720.96 L1577.1 1720.96 L1576.82 1720.96 L1576.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1576.82,1720.96 1576.82,1720.96 1577.1,1720.96 1576.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1577.1 1720.96 L1577.1 1720.96 L1577.38 1720.96 L1577.38 1720.96 L1577.1 1720.96 L1577.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1577.1,1720.96 1577.1,1720.96 1577.38,1720.96 1577.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1577.38 1720.96 L1577.38 1720.96 L1577.66 1720.96 L1577.66 1720.96 L1577.38 1720.96 L1577.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1577.38,1720.96 1577.38,1720.96 1577.66,1720.96 1577.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1577.66 1720.96 L1577.66 1720.96 L1577.94 1720.96 L1577.94 1720.96 L1577.66 1720.96 L1577.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1577.66,1720.96 1577.66,1720.96 1577.94,1720.96 1577.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1577.94 1720.76 L1577.94 1720.96 L1578.22 1720.96 L1578.22 1720.76 L1577.94 1720.76 L1577.94 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1577.94,1720.76 1577.94,1720.96 1578.22,1720.96 1578.22,1720.76 1577.94,1720.76 "/>
<path clip-path="url(#clip322)" d="M1578.22 1720.96 L1578.22 1720.96 L1578.51 1720.96 L1578.51 1720.96 L1578.22 1720.96 L1578.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1578.22,1720.96 1578.22,1720.96 1578.51,1720.96 1578.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1578.51 1720.96 L1578.51 1720.96 L1578.79 1720.96 L1578.79 1720.96 L1578.51 1720.96 L1578.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1578.51,1720.96 1578.51,1720.96 1578.79,1720.96 1578.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1578.79 1720.96 L1578.79 1720.96 L1579.07 1720.96 L1579.07 1720.96 L1578.79 1720.96 L1578.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1578.79,1720.96 1578.79,1720.96 1579.07,1720.96 1578.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1579.07 1720.96 L1579.07 1720.96 L1579.35 1720.96 L1579.35 1720.96 L1579.07 1720.96 L1579.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1579.07,1720.96 1579.07,1720.96 1579.35,1720.96 1579.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1579.35 1720.96 L1579.35 1720.96 L1579.63 1720.96 L1579.63 1720.96 L1579.35 1720.96 L1579.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1579.35,1720.96 1579.35,1720.96 1579.63,1720.96 1579.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1579.63 1720.96 L1579.63 1720.96 L1579.91 1720.96 L1579.91 1720.96 L1579.63 1720.96 L1579.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1579.63,1720.96 1579.63,1720.96 1579.91,1720.96 1579.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1579.91 1720.96 L1579.91 1720.96 L1580.2 1720.96 L1580.2 1720.96 L1579.91 1720.96 L1579.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1579.91,1720.96 1579.91,1720.96 1580.2,1720.96 1579.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1580.2 1720.96 L1580.2 1720.96 L1580.48 1720.96 L1580.48 1720.96 L1580.2 1720.96 L1580.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1580.2,1720.96 1580.2,1720.96 1580.48,1720.96 1580.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1580.48 1720.96 L1580.48 1720.96 L1580.76 1720.96 L1580.76 1720.96 L1580.48 1720.96 L1580.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1580.48,1720.96 1580.48,1720.96 1580.76,1720.96 1580.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1580.76 1720.96 L1580.76 1720.96 L1581.04 1720.96 L1581.04 1720.96 L1580.76 1720.96 L1580.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1580.76,1720.96 1580.76,1720.96 1581.04,1720.96 1580.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1581.04 1720.96 L1581.04 1720.96 L1581.32 1720.96 L1581.32 1720.96 L1581.04 1720.96 L1581.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1581.04,1720.96 1581.04,1720.96 1581.32,1720.96 1581.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1581.32 1720.96 L1581.32 1720.96 L1581.61 1720.96 L1581.61 1720.96 L1581.32 1720.96 L1581.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1581.32,1720.96 1581.32,1720.96 1581.61,1720.96 1581.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1581.61 1720.96 L1581.61 1720.96 L1581.89 1720.96 L1581.89 1720.96 L1581.61 1720.96 L1581.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1581.61,1720.96 1581.61,1720.96 1581.89,1720.96 1581.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1581.89 1720.96 L1581.89 1720.96 L1582.17 1720.96 L1582.17 1720.96 L1581.89 1720.96 L1581.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1581.89,1720.96 1581.89,1720.96 1582.17,1720.96 1581.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1582.17 1720.96 L1582.17 1720.96 L1582.45 1720.96 L1582.45 1720.96 L1582.17 1720.96 L1582.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1582.17,1720.96 1582.17,1720.96 1582.45,1720.96 1582.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1582.45 1720.96 L1582.45 1720.96 L1582.73 1720.96 L1582.73 1720.96 L1582.45 1720.96 L1582.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1582.45,1720.96 1582.45,1720.96 1582.73,1720.96 1582.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1582.73 1720.96 L1582.73 1720.96 L1583.01 1720.96 L1583.01 1720.96 L1582.73 1720.96 L1582.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1582.73,1720.96 1582.73,1720.96 1583.01,1720.96 1582.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1583.01 1720.96 L1583.01 1720.96 L1583.3 1720.96 L1583.3 1720.96 L1583.01 1720.96 L1583.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1583.01,1720.96 1583.01,1720.96 1583.3,1720.96 1583.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1583.3 1720.96 L1583.3 1720.96 L1583.58 1720.96 L1583.58 1720.96 L1583.3 1720.96 L1583.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1583.3,1720.96 1583.3,1720.96 1583.58,1720.96 1583.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1583.58 1720.96 L1583.58 1720.96 L1583.86 1720.96 L1583.86 1720.96 L1583.58 1720.96 L1583.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1583.58,1720.96 1583.58,1720.96 1583.86,1720.96 1583.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1583.86 1720.96 L1583.86 1720.96 L1584.14 1720.96 L1584.14 1720.96 L1583.86 1720.96 L1583.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1583.86,1720.96 1583.86,1720.96 1584.14,1720.96 1583.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1584.14 1720.96 L1584.14 1720.96 L1584.42 1720.96 L1584.42 1720.96 L1584.14 1720.96 L1584.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1584.14,1720.96 1584.14,1720.96 1584.42,1720.96 1584.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1584.42 1720.96 L1584.42 1720.96 L1584.7 1720.96 L1584.7 1720.96 L1584.42 1720.96 L1584.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1584.42,1720.96 1584.42,1720.96 1584.7,1720.96 1584.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1584.7 1720.96 L1584.7 1720.96 L1584.99 1720.96 L1584.99 1720.96 L1584.7 1720.96 L1584.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1584.7,1720.96 1584.7,1720.96 1584.99,1720.96 1584.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1584.99 1720.96 L1584.99 1720.96 L1585.27 1720.96 L1585.27 1720.96 L1584.99 1720.96 L1584.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1584.99,1720.96 1584.99,1720.96 1585.27,1720.96 1584.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1585.27 1720.96 L1585.27 1720.96 L1585.55 1720.96 L1585.55 1720.96 L1585.27 1720.96 L1585.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1585.27,1720.96 1585.27,1720.96 1585.55,1720.96 1585.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1585.55 1720.96 L1585.55 1720.96 L1585.83 1720.96 L1585.83 1720.96 L1585.55 1720.96 L1585.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1585.55,1720.96 1585.55,1720.96 1585.83,1720.96 1585.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1585.83 1720.96 L1585.83 1720.96 L1586.11 1720.96 L1586.11 1720.96 L1585.83 1720.96 L1585.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1585.83,1720.96 1585.83,1720.96 1586.11,1720.96 1585.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1586.11 1720.96 L1586.11 1720.96 L1586.39 1720.96 L1586.39 1720.96 L1586.11 1720.96 L1586.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1586.11,1720.96 1586.11,1720.96 1586.39,1720.96 1586.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1586.39 1720.96 L1586.39 1720.96 L1586.68 1720.96 L1586.68 1720.96 L1586.39 1720.96 L1586.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1586.39,1720.96 1586.39,1720.96 1586.68,1720.96 1586.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1586.68 1720.96 L1586.68 1720.96 L1586.96 1720.96 L1586.96 1720.96 L1586.68 1720.96 L1586.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1586.68,1720.96 1586.68,1720.96 1586.96,1720.96 1586.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1586.96 1720.96 L1586.96 1720.96 L1587.24 1720.96 L1587.24 1720.96 L1586.96 1720.96 L1586.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1586.96,1720.96 1586.96,1720.96 1587.24,1720.96 1586.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1587.24 1720.96 L1587.24 1720.96 L1587.52 1720.96 L1587.52 1720.96 L1587.24 1720.96 L1587.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1587.24,1720.96 1587.24,1720.96 1587.52,1720.96 1587.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1587.52 1720.96 L1587.52 1720.96 L1587.8 1720.96 L1587.8 1720.96 L1587.52 1720.96 L1587.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1587.52,1720.96 1587.52,1720.96 1587.8,1720.96 1587.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1587.8 1720.96 L1587.8 1720.96 L1588.09 1720.96 L1588.09 1720.96 L1587.8 1720.96 L1587.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1587.8,1720.96 1587.8,1720.96 1588.09,1720.96 1587.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1588.09 1720.96 L1588.09 1720.96 L1588.37 1720.96 L1588.37 1720.96 L1588.09 1720.96 L1588.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1588.09,1720.96 1588.09,1720.96 1588.37,1720.96 1588.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1588.37 1720.96 L1588.37 1720.96 L1588.65 1720.96 L1588.65 1720.96 L1588.37 1720.96 L1588.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1588.37,1720.96 1588.37,1720.96 1588.65,1720.96 1588.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1588.65 1720.96 L1588.65 1720.96 L1588.93 1720.96 L1588.93 1720.96 L1588.65 1720.96 L1588.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1588.65,1720.96 1588.65,1720.96 1588.93,1720.96 1588.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1588.93 1720.96 L1588.93 1720.96 L1589.21 1720.96 L1589.21 1720.96 L1588.93 1720.96 L1588.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1588.93,1720.96 1588.93,1720.96 1589.21,1720.96 1588.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1589.21 1720.96 L1589.21 1720.96 L1589.49 1720.96 L1589.49 1720.96 L1589.21 1720.96 L1589.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1589.21,1720.96 1589.21,1720.96 1589.49,1720.96 1589.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1589.49 1720.96 L1589.49 1720.96 L1589.78 1720.96 L1589.78 1720.96 L1589.49 1720.96 L1589.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1589.49,1720.96 1589.49,1720.96 1589.78,1720.96 1589.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1589.78 1720.96 L1589.78 1720.96 L1590.06 1720.96 L1590.06 1720.96 L1589.78 1720.96 L1589.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1589.78,1720.96 1589.78,1720.96 1590.06,1720.96 1589.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1590.06 1720.96 L1590.06 1720.96 L1590.34 1720.96 L1590.34 1720.96 L1590.06 1720.96 L1590.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1590.06,1720.96 1590.06,1720.96 1590.34,1720.96 1590.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1590.34 1720.96 L1590.34 1720.96 L1590.62 1720.96 L1590.62 1720.96 L1590.34 1720.96 L1590.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1590.34,1720.96 1590.34,1720.96 1590.62,1720.96 1590.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1590.62 1720.96 L1590.62 1720.96 L1590.9 1720.96 L1590.9 1720.96 L1590.62 1720.96 L1590.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1590.62,1720.96 1590.62,1720.96 1590.9,1720.96 1590.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1590.9 1720.96 L1590.9 1720.96 L1591.18 1720.96 L1591.18 1720.96 L1590.9 1720.96 L1590.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1590.9,1720.96 1590.9,1720.96 1591.18,1720.96 1590.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1591.18 1720.96 L1591.18 1720.96 L1591.47 1720.96 L1591.47 1720.96 L1591.18 1720.96 L1591.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1591.18,1720.96 1591.18,1720.96 1591.47,1720.96 1591.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1591.47 1720.96 L1591.47 1720.96 L1591.75 1720.96 L1591.75 1720.96 L1591.47 1720.96 L1591.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1591.47,1720.96 1591.47,1720.96 1591.75,1720.96 1591.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1591.75 1720.96 L1591.75 1720.96 L1592.03 1720.96 L1592.03 1720.96 L1591.75 1720.96 L1591.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1591.75,1720.96 1591.75,1720.96 1592.03,1720.96 1591.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1592.03 1720.96 L1592.03 1720.96 L1592.31 1720.96 L1592.31 1720.96 L1592.03 1720.96 L1592.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1592.03,1720.96 1592.03,1720.96 1592.31,1720.96 1592.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1592.31 1720.96 L1592.31 1720.96 L1592.59 1720.96 L1592.59 1720.96 L1592.31 1720.96 L1592.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1592.31,1720.96 1592.31,1720.96 1592.59,1720.96 1592.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1592.59 1720.96 L1592.59 1720.96 L1592.87 1720.96 L1592.87 1720.96 L1592.59 1720.96 L1592.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1592.59,1720.96 1592.59,1720.96 1592.87,1720.96 1592.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1592.87 1720.96 L1592.87 1720.96 L1593.16 1720.96 L1593.16 1720.96 L1592.87 1720.96 L1592.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1592.87,1720.96 1592.87,1720.96 1593.16,1720.96 1592.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1593.16 1720.76 L1593.16 1720.96 L1593.44 1720.96 L1593.44 1720.76 L1593.16 1720.76 L1593.16 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1593.16,1720.76 1593.16,1720.96 1593.44,1720.96 1593.44,1720.76 1593.16,1720.76 "/>
<path clip-path="url(#clip322)" d="M1593.44 1720.96 L1593.44 1720.96 L1593.72 1720.96 L1593.72 1720.96 L1593.44 1720.96 L1593.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1593.44,1720.96 1593.44,1720.96 1593.72,1720.96 1593.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1593.72 1720.96 L1593.72 1720.96 L1594 1720.96 L1594 1720.96 L1593.72 1720.96 L1593.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1593.72,1720.96 1593.72,1720.96 1594,1720.96 1593.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1594 1720.96 L1594 1720.96 L1594.28 1720.96 L1594.28 1720.96 L1594 1720.96 L1594 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1594,1720.96 1594,1720.96 1594.28,1720.96 1594,1720.96 "/>
<path clip-path="url(#clip322)" d="M1594.28 1720.96 L1594.28 1720.96 L1594.56 1720.96 L1594.56 1720.96 L1594.28 1720.96 L1594.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1594.28,1720.96 1594.28,1720.96 1594.56,1720.96 1594.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1594.56 1720.96 L1594.56 1720.96 L1594.85 1720.96 L1594.85 1720.96 L1594.56 1720.96 L1594.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1594.56,1720.96 1594.56,1720.96 1594.85,1720.96 1594.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1594.85 1720.96 L1594.85 1720.96 L1595.13 1720.96 L1595.13 1720.96 L1594.85 1720.96 L1594.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1594.85,1720.96 1594.85,1720.96 1595.13,1720.96 1594.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1595.13 1720.96 L1595.13 1720.96 L1595.41 1720.96 L1595.41 1720.96 L1595.13 1720.96 L1595.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1595.13,1720.96 1595.13,1720.96 1595.41,1720.96 1595.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1595.41 1720.96 L1595.41 1720.96 L1595.69 1720.96 L1595.69 1720.96 L1595.41 1720.96 L1595.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1595.41,1720.96 1595.41,1720.96 1595.69,1720.96 1595.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1595.69 1720.96 L1595.69 1720.96 L1595.97 1720.96 L1595.97 1720.96 L1595.69 1720.96 L1595.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1595.69,1720.96 1595.69,1720.96 1595.97,1720.96 1595.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1595.97 1720.96 L1595.97 1720.96 L1596.26 1720.96 L1596.26 1720.96 L1595.97 1720.96 L1595.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1595.97,1720.96 1595.97,1720.96 1596.26,1720.96 1595.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1596.26 1720.96 L1596.26 1720.96 L1596.54 1720.96 L1596.54 1720.96 L1596.26 1720.96 L1596.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1596.26,1720.96 1596.26,1720.96 1596.54,1720.96 1596.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1596.54 1720.96 L1596.54 1720.96 L1596.82 1720.96 L1596.82 1720.96 L1596.54 1720.96 L1596.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1596.54,1720.96 1596.54,1720.96 1596.82,1720.96 1596.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1596.82 1720.96 L1596.82 1720.96 L1597.1 1720.96 L1597.1 1720.96 L1596.82 1720.96 L1596.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1596.82,1720.96 1596.82,1720.96 1597.1,1720.96 1596.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1597.1 1720.96 L1597.1 1720.96 L1597.38 1720.96 L1597.38 1720.96 L1597.1 1720.96 L1597.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1597.1,1720.96 1597.1,1720.96 1597.38,1720.96 1597.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1597.38 1720.96 L1597.38 1720.96 L1597.66 1720.96 L1597.66 1720.96 L1597.38 1720.96 L1597.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1597.38,1720.96 1597.38,1720.96 1597.66,1720.96 1597.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1597.66 1720.96 L1597.66 1720.96 L1597.95 1720.96 L1597.95 1720.96 L1597.66 1720.96 L1597.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1597.66,1720.96 1597.66,1720.96 1597.95,1720.96 1597.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1597.95 1720.96 L1597.95 1720.96 L1598.23 1720.96 L1598.23 1720.96 L1597.95 1720.96 L1597.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1597.95,1720.96 1597.95,1720.96 1598.23,1720.96 1597.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1598.23 1720.96 L1598.23 1720.96 L1598.51 1720.96 L1598.51 1720.96 L1598.23 1720.96 L1598.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1598.23,1720.96 1598.23,1720.96 1598.51,1720.96 1598.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1598.51 1720.96 L1598.51 1720.96 L1598.79 1720.96 L1598.79 1720.96 L1598.51 1720.96 L1598.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1598.51,1720.96 1598.51,1720.96 1598.79,1720.96 1598.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1598.79 1720.96 L1598.79 1720.96 L1599.07 1720.96 L1599.07 1720.96 L1598.79 1720.96 L1598.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1598.79,1720.96 1598.79,1720.96 1599.07,1720.96 1598.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1599.07 1720.96 L1599.07 1720.96 L1599.35 1720.96 L1599.35 1720.96 L1599.07 1720.96 L1599.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1599.07,1720.96 1599.07,1720.96 1599.35,1720.96 1599.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1599.35 1720.96 L1599.35 1720.96 L1599.64 1720.96 L1599.64 1720.96 L1599.35 1720.96 L1599.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1599.35,1720.96 1599.35,1720.96 1599.64,1720.96 1599.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1599.64 1720.96 L1599.64 1720.96 L1599.92 1720.96 L1599.92 1720.96 L1599.64 1720.96 L1599.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1599.64,1720.96 1599.64,1720.96 1599.92,1720.96 1599.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1599.92 1720.96 L1599.92 1720.96 L1600.2 1720.96 L1600.2 1720.96 L1599.92 1720.96 L1599.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1599.92,1720.96 1599.92,1720.96 1600.2,1720.96 1599.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1600.2 1720.96 L1600.2 1720.96 L1600.48 1720.96 L1600.48 1720.96 L1600.2 1720.96 L1600.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1600.2,1720.96 1600.2,1720.96 1600.48,1720.96 1600.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1600.48 1720.96 L1600.48 1720.96 L1600.76 1720.96 L1600.76 1720.96 L1600.48 1720.96 L1600.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1600.48,1720.96 1600.48,1720.96 1600.76,1720.96 1600.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1600.76 1720.96 L1600.76 1720.96 L1601.04 1720.96 L1601.04 1720.96 L1600.76 1720.96 L1600.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1600.76,1720.96 1600.76,1720.96 1601.04,1720.96 1600.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1601.04 1720.96 L1601.04 1720.96 L1601.33 1720.96 L1601.33 1720.96 L1601.04 1720.96 L1601.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1601.04,1720.96 1601.04,1720.96 1601.33,1720.96 1601.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1601.33 1720.96 L1601.33 1720.96 L1601.61 1720.96 L1601.61 1720.96 L1601.33 1720.96 L1601.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1601.33,1720.96 1601.33,1720.96 1601.61,1720.96 1601.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1601.61 1720.96 L1601.61 1720.96 L1601.89 1720.96 L1601.89 1720.96 L1601.61 1720.96 L1601.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1601.61,1720.96 1601.61,1720.96 1601.89,1720.96 1601.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1601.89 1720.96 L1601.89 1720.96 L1602.17 1720.96 L1602.17 1720.96 L1601.89 1720.96 L1601.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1601.89,1720.96 1601.89,1720.96 1602.17,1720.96 1601.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1602.17 1720.96 L1602.17 1720.96 L1602.45 1720.96 L1602.45 1720.96 L1602.17 1720.96 L1602.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1602.17,1720.96 1602.17,1720.96 1602.45,1720.96 1602.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1602.45 1720.96 L1602.45 1720.96 L1602.73 1720.96 L1602.73 1720.96 L1602.45 1720.96 L1602.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1602.45,1720.96 1602.45,1720.96 1602.73,1720.96 1602.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1602.73 1720.96 L1602.73 1720.96 L1603.02 1720.96 L1603.02 1720.96 L1602.73 1720.96 L1602.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1602.73,1720.96 1602.73,1720.96 1603.02,1720.96 1602.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1603.02 1720.96 L1603.02 1720.96 L1603.3 1720.96 L1603.3 1720.96 L1603.02 1720.96 L1603.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1603.02,1720.96 1603.02,1720.96 1603.3,1720.96 1603.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1603.3 1720.96 L1603.3 1720.96 L1603.58 1720.96 L1603.58 1720.96 L1603.3 1720.96 L1603.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1603.3,1720.96 1603.3,1720.96 1603.58,1720.96 1603.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1603.58 1720.96 L1603.58 1720.96 L1603.86 1720.96 L1603.86 1720.96 L1603.58 1720.96 L1603.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1603.58,1720.96 1603.58,1720.96 1603.86,1720.96 1603.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1603.86 1720.96 L1603.86 1720.96 L1604.14 1720.96 L1604.14 1720.96 L1603.86 1720.96 L1603.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1603.86,1720.96 1603.86,1720.96 1604.14,1720.96 1603.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1604.14 1720.96 L1604.14 1720.96 L1604.43 1720.96 L1604.43 1720.96 L1604.14 1720.96 L1604.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1604.14,1720.96 1604.14,1720.96 1604.43,1720.96 1604.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1604.43 1720.96 L1604.43 1720.96 L1604.71 1720.96 L1604.71 1720.96 L1604.43 1720.96 L1604.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1604.43,1720.96 1604.43,1720.96 1604.71,1720.96 1604.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1604.71 1720.96 L1604.71 1720.96 L1604.99 1720.96 L1604.99 1720.96 L1604.71 1720.96 L1604.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1604.71,1720.96 1604.71,1720.96 1604.99,1720.96 1604.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1604.99 1720.96 L1604.99 1720.96 L1605.27 1720.96 L1605.27 1720.96 L1604.99 1720.96 L1604.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1604.99,1720.96 1604.99,1720.96 1605.27,1720.96 1604.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1605.27 1720.96 L1605.27 1720.96 L1605.55 1720.96 L1605.55 1720.96 L1605.27 1720.96 L1605.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1605.27,1720.96 1605.27,1720.96 1605.55,1720.96 1605.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1605.55 1720.96 L1605.55 1720.96 L1605.83 1720.96 L1605.83 1720.96 L1605.55 1720.96 L1605.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1605.55,1720.96 1605.55,1720.96 1605.83,1720.96 1605.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1605.83 1720.96 L1605.83 1720.96 L1606.12 1720.96 L1606.12 1720.96 L1605.83 1720.96 L1605.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1605.83,1720.96 1605.83,1720.96 1606.12,1720.96 1605.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1606.12 1720.96 L1606.12 1720.96 L1606.4 1720.96 L1606.4 1720.96 L1606.12 1720.96 L1606.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1606.12,1720.96 1606.12,1720.96 1606.4,1720.96 1606.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1606.4 1720.96 L1606.4 1720.96 L1606.68 1720.96 L1606.68 1720.96 L1606.4 1720.96 L1606.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1606.4,1720.96 1606.4,1720.96 1606.68,1720.96 1606.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1606.68 1720.96 L1606.68 1720.96 L1606.96 1720.96 L1606.96 1720.96 L1606.68 1720.96 L1606.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1606.68,1720.96 1606.68,1720.96 1606.96,1720.96 1606.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1606.96 1720.96 L1606.96 1720.96 L1607.24 1720.96 L1607.24 1720.96 L1606.96 1720.96 L1606.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1606.96,1720.96 1606.96,1720.96 1607.24,1720.96 1606.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1607.24 1720.96 L1607.24 1720.96 L1607.52 1720.96 L1607.52 1720.96 L1607.24 1720.96 L1607.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1607.24,1720.96 1607.24,1720.96 1607.52,1720.96 1607.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1607.52 1720.96 L1607.52 1720.96 L1607.81 1720.96 L1607.81 1720.96 L1607.52 1720.96 L1607.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1607.52,1720.96 1607.52,1720.96 1607.81,1720.96 1607.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1607.81 1720.96 L1607.81 1720.96 L1608.09 1720.96 L1608.09 1720.96 L1607.81 1720.96 L1607.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1607.81,1720.96 1607.81,1720.96 1608.09,1720.96 1607.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1608.09 1720.96 L1608.09 1720.96 L1608.37 1720.96 L1608.37 1720.96 L1608.09 1720.96 L1608.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1608.09,1720.96 1608.09,1720.96 1608.37,1720.96 1608.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1608.37 1720.96 L1608.37 1720.96 L1608.65 1720.96 L1608.65 1720.96 L1608.37 1720.96 L1608.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1608.37,1720.96 1608.37,1720.96 1608.65,1720.96 1608.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1608.65 1720.96 L1608.65 1720.96 L1608.93 1720.96 L1608.93 1720.96 L1608.65 1720.96 L1608.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1608.65,1720.96 1608.65,1720.96 1608.93,1720.96 1608.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1608.93 1720.96 L1608.93 1720.96 L1609.21 1720.96 L1609.21 1720.96 L1608.93 1720.96 L1608.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1608.93,1720.96 1608.93,1720.96 1609.21,1720.96 1608.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1609.21 1720.96 L1609.21 1720.96 L1609.5 1720.96 L1609.5 1720.96 L1609.21 1720.96 L1609.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1609.21,1720.96 1609.21,1720.96 1609.5,1720.96 1609.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1609.5 1720.96 L1609.5 1720.96 L1609.78 1720.96 L1609.78 1720.96 L1609.5 1720.96 L1609.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1609.5,1720.96 1609.5,1720.96 1609.78,1720.96 1609.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1609.78 1720.96 L1609.78 1720.96 L1610.06 1720.96 L1610.06 1720.96 L1609.78 1720.96 L1609.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1609.78,1720.96 1609.78,1720.96 1610.06,1720.96 1609.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1610.06 1720.96 L1610.06 1720.96 L1610.34 1720.96 L1610.34 1720.96 L1610.06 1720.96 L1610.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1610.06,1720.96 1610.06,1720.96 1610.34,1720.96 1610.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1610.34 1720.96 L1610.34 1720.96 L1610.62 1720.96 L1610.62 1720.96 L1610.34 1720.96 L1610.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1610.34,1720.96 1610.34,1720.96 1610.62,1720.96 1610.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1610.62 1720.96 L1610.62 1720.96 L1610.9 1720.96 L1610.9 1720.96 L1610.62 1720.96 L1610.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1610.62,1720.96 1610.62,1720.96 1610.9,1720.96 1610.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1610.9 1720.96 L1610.9 1720.96 L1611.19 1720.96 L1611.19 1720.96 L1610.9 1720.96 L1610.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1610.9,1720.96 1610.9,1720.96 1611.19,1720.96 1610.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1611.19 1720.96 L1611.19 1720.96 L1611.47 1720.96 L1611.47 1720.96 L1611.19 1720.96 L1611.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1611.19,1720.96 1611.19,1720.96 1611.47,1720.96 1611.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1611.47 1720.96 L1611.47 1720.96 L1611.75 1720.96 L1611.75 1720.96 L1611.47 1720.96 L1611.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1611.47,1720.96 1611.47,1720.96 1611.75,1720.96 1611.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1611.75 1720.96 L1611.75 1720.96 L1612.03 1720.96 L1612.03 1720.96 L1611.75 1720.96 L1611.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1611.75,1720.96 1611.75,1720.96 1612.03,1720.96 1611.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1612.03 1720.96 L1612.03 1720.96 L1612.31 1720.96 L1612.31 1720.96 L1612.03 1720.96 L1612.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1612.03,1720.96 1612.03,1720.96 1612.31,1720.96 1612.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1612.31 1720.96 L1612.31 1720.96 L1612.6 1720.96 L1612.6 1720.96 L1612.31 1720.96 L1612.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1612.31,1720.96 1612.31,1720.96 1612.6,1720.96 1612.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1612.6 1720.96 L1612.6 1720.96 L1612.88 1720.96 L1612.88 1720.96 L1612.6 1720.96 L1612.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1612.6,1720.96 1612.6,1720.96 1612.88,1720.96 1612.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1612.88 1720.96 L1612.88 1720.96 L1613.16 1720.96 L1613.16 1720.96 L1612.88 1720.96 L1612.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1612.88,1720.96 1612.88,1720.96 1613.16,1720.96 1612.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1613.16 1720.96 L1613.16 1720.96 L1613.44 1720.96 L1613.44 1720.96 L1613.16 1720.96 L1613.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1613.16,1720.96 1613.16,1720.96 1613.44,1720.96 1613.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1613.44 1720.76 L1613.44 1720.96 L1613.72 1720.96 L1613.72 1720.76 L1613.44 1720.76 L1613.44 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1613.44,1720.76 1613.44,1720.96 1613.72,1720.96 1613.72,1720.76 1613.44,1720.76 "/>
<path clip-path="url(#clip322)" d="M1613.72 1720.96 L1613.72 1720.96 L1614 1720.96 L1614 1720.96 L1613.72 1720.96 L1613.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1613.72,1720.96 1613.72,1720.96 1614,1720.96 1613.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1614 1720.96 L1614 1720.96 L1614.29 1720.96 L1614.29 1720.96 L1614 1720.96 L1614 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1614,1720.96 1614,1720.96 1614.29,1720.96 1614,1720.96 "/>
<path clip-path="url(#clip322)" d="M1614.29 1720.96 L1614.29 1720.96 L1614.57 1720.96 L1614.57 1720.96 L1614.29 1720.96 L1614.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1614.29,1720.96 1614.29,1720.96 1614.57,1720.96 1614.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1614.57 1720.96 L1614.57 1720.96 L1614.85 1720.96 L1614.85 1720.96 L1614.57 1720.96 L1614.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1614.57,1720.96 1614.57,1720.96 1614.85,1720.96 1614.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1614.85 1720.96 L1614.85 1720.96 L1615.13 1720.96 L1615.13 1720.96 L1614.85 1720.96 L1614.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1614.85,1720.96 1614.85,1720.96 1615.13,1720.96 1614.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1615.13 1720.96 L1615.13 1720.96 L1615.41 1720.96 L1615.41 1720.96 L1615.13 1720.96 L1615.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1615.13,1720.96 1615.13,1720.96 1615.41,1720.96 1615.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1615.41 1720.96 L1615.41 1720.96 L1615.69 1720.96 L1615.69 1720.96 L1615.41 1720.96 L1615.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1615.41,1720.96 1615.41,1720.96 1615.69,1720.96 1615.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1615.69 1720.96 L1615.69 1720.96 L1615.98 1720.96 L1615.98 1720.96 L1615.69 1720.96 L1615.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1615.69,1720.96 1615.69,1720.96 1615.98,1720.96 1615.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1615.98 1720.96 L1615.98 1720.96 L1616.26 1720.96 L1616.26 1720.96 L1615.98 1720.96 L1615.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1615.98,1720.96 1615.98,1720.96 1616.26,1720.96 1615.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1616.26 1720.96 L1616.26 1720.96 L1616.54 1720.96 L1616.54 1720.96 L1616.26 1720.96 L1616.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1616.26,1720.96 1616.26,1720.96 1616.54,1720.96 1616.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1616.54 1720.96 L1616.54 1720.96 L1616.82 1720.96 L1616.82 1720.96 L1616.54 1720.96 L1616.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1616.54,1720.96 1616.54,1720.96 1616.82,1720.96 1616.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1616.82 1720.96 L1616.82 1720.96 L1617.1 1720.96 L1617.1 1720.96 L1616.82 1720.96 L1616.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1616.82,1720.96 1616.82,1720.96 1617.1,1720.96 1616.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1617.1 1720.96 L1617.1 1720.96 L1617.38 1720.96 L1617.38 1720.96 L1617.1 1720.96 L1617.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1617.1,1720.96 1617.1,1720.96 1617.38,1720.96 1617.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1617.38 1720.96 L1617.38 1720.96 L1617.67 1720.96 L1617.67 1720.96 L1617.38 1720.96 L1617.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1617.38,1720.96 1617.38,1720.96 1617.67,1720.96 1617.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1617.67 1720.96 L1617.67 1720.96 L1617.95 1720.96 L1617.95 1720.96 L1617.67 1720.96 L1617.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1617.67,1720.96 1617.67,1720.96 1617.95,1720.96 1617.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1617.95 1720.96 L1617.95 1720.96 L1618.23 1720.96 L1618.23 1720.96 L1617.95 1720.96 L1617.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1617.95,1720.96 1617.95,1720.96 1618.23,1720.96 1617.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1618.23 1720.96 L1618.23 1720.96 L1618.51 1720.96 L1618.51 1720.96 L1618.23 1720.96 L1618.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1618.23,1720.96 1618.23,1720.96 1618.51,1720.96 1618.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1618.51 1720.96 L1618.51 1720.96 L1618.79 1720.96 L1618.79 1720.96 L1618.51 1720.96 L1618.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1618.51,1720.96 1618.51,1720.96 1618.79,1720.96 1618.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1618.79 1720.96 L1618.79 1720.96 L1619.07 1720.96 L1619.07 1720.96 L1618.79 1720.96 L1618.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1618.79,1720.96 1618.79,1720.96 1619.07,1720.96 1618.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1619.07 1720.96 L1619.07 1720.96 L1619.36 1720.96 L1619.36 1720.96 L1619.07 1720.96 L1619.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1619.07,1720.96 1619.07,1720.96 1619.36,1720.96 1619.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1619.36 1720.96 L1619.36 1720.96 L1619.64 1720.96 L1619.64 1720.96 L1619.36 1720.96 L1619.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1619.36,1720.96 1619.36,1720.96 1619.64,1720.96 1619.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1619.64 1720.96 L1619.64 1720.96 L1619.92 1720.96 L1619.92 1720.96 L1619.64 1720.96 L1619.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1619.64,1720.96 1619.64,1720.96 1619.92,1720.96 1619.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1619.92 1720.96 L1619.92 1720.96 L1620.2 1720.96 L1620.2 1720.96 L1619.92 1720.96 L1619.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1619.92,1720.96 1619.92,1720.96 1620.2,1720.96 1619.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1620.2 1720.96 L1620.2 1720.96 L1620.48 1720.96 L1620.48 1720.96 L1620.2 1720.96 L1620.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1620.2,1720.96 1620.2,1720.96 1620.48,1720.96 1620.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1620.48 1720.96 L1620.48 1720.96 L1620.77 1720.96 L1620.77 1720.96 L1620.48 1720.96 L1620.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1620.48,1720.96 1620.48,1720.96 1620.77,1720.96 1620.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1620.77 1720.96 L1620.77 1720.96 L1621.05 1720.96 L1621.05 1720.96 L1620.77 1720.96 L1620.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1620.77,1720.96 1620.77,1720.96 1621.05,1720.96 1620.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1621.05 1720.96 L1621.05 1720.96 L1621.33 1720.96 L1621.33 1720.96 L1621.05 1720.96 L1621.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1621.05,1720.96 1621.05,1720.96 1621.33,1720.96 1621.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1621.33 1720.96 L1621.33 1720.96 L1621.61 1720.96 L1621.61 1720.96 L1621.33 1720.96 L1621.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1621.33,1720.96 1621.33,1720.96 1621.61,1720.96 1621.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1621.61 1720.96 L1621.61 1720.96 L1621.89 1720.96 L1621.89 1720.96 L1621.61 1720.96 L1621.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1621.61,1720.96 1621.61,1720.96 1621.89,1720.96 1621.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1621.89 1720.96 L1621.89 1720.96 L1622.17 1720.96 L1622.17 1720.96 L1621.89 1720.96 L1621.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1621.89,1720.96 1621.89,1720.96 1622.17,1720.96 1621.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1622.17 1720.96 L1622.17 1720.96 L1622.46 1720.96 L1622.46 1720.96 L1622.17 1720.96 L1622.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1622.17,1720.96 1622.17,1720.96 1622.46,1720.96 1622.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1622.46 1720.96 L1622.46 1720.96 L1622.74 1720.96 L1622.74 1720.96 L1622.46 1720.96 L1622.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1622.46,1720.96 1622.46,1720.96 1622.74,1720.96 1622.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1622.74 1720.96 L1622.74 1720.96 L1623.02 1720.96 L1623.02 1720.96 L1622.74 1720.96 L1622.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1622.74,1720.96 1622.74,1720.96 1623.02,1720.96 1622.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1623.02 1720.96 L1623.02 1720.96 L1623.3 1720.96 L1623.3 1720.96 L1623.02 1720.96 L1623.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1623.02,1720.96 1623.02,1720.96 1623.3,1720.96 1623.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1623.3 1720.96 L1623.3 1720.96 L1623.58 1720.96 L1623.58 1720.96 L1623.3 1720.96 L1623.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1623.3,1720.96 1623.3,1720.96 1623.58,1720.96 1623.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1623.58 1720.96 L1623.58 1720.96 L1623.86 1720.96 L1623.86 1720.96 L1623.58 1720.96 L1623.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1623.58,1720.96 1623.58,1720.96 1623.86,1720.96 1623.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1623.86 1720.96 L1623.86 1720.96 L1624.15 1720.96 L1624.15 1720.96 L1623.86 1720.96 L1623.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1623.86,1720.96 1623.86,1720.96 1624.15,1720.96 1623.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1624.15 1720.96 L1624.15 1720.96 L1624.43 1720.96 L1624.43 1720.96 L1624.15 1720.96 L1624.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1624.15,1720.96 1624.15,1720.96 1624.43,1720.96 1624.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1624.43 1720.96 L1624.43 1720.96 L1624.71 1720.96 L1624.71 1720.96 L1624.43 1720.96 L1624.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1624.43,1720.96 1624.43,1720.96 1624.71,1720.96 1624.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1624.71 1720.96 L1624.71 1720.96 L1624.99 1720.96 L1624.99 1720.96 L1624.71 1720.96 L1624.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1624.71,1720.96 1624.71,1720.96 1624.99,1720.96 1624.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1624.99 1720.96 L1624.99 1720.96 L1625.27 1720.96 L1625.27 1720.96 L1624.99 1720.96 L1624.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1624.99,1720.96 1624.99,1720.96 1625.27,1720.96 1624.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1625.27 1720.96 L1625.27 1720.96 L1625.55 1720.96 L1625.55 1720.96 L1625.27 1720.96 L1625.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1625.27,1720.96 1625.27,1720.96 1625.55,1720.96 1625.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1625.55 1720.96 L1625.55 1720.96 L1625.84 1720.96 L1625.84 1720.96 L1625.55 1720.96 L1625.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1625.55,1720.96 1625.55,1720.96 1625.84,1720.96 1625.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1625.84 1720.96 L1625.84 1720.96 L1626.12 1720.96 L1626.12 1720.96 L1625.84 1720.96 L1625.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1625.84,1720.96 1625.84,1720.96 1626.12,1720.96 1625.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1626.12 1720.96 L1626.12 1720.96 L1626.4 1720.96 L1626.4 1720.96 L1626.12 1720.96 L1626.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1626.12,1720.96 1626.12,1720.96 1626.4,1720.96 1626.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1626.4 1720.96 L1626.4 1720.96 L1626.68 1720.96 L1626.68 1720.96 L1626.4 1720.96 L1626.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1626.4,1720.96 1626.4,1720.96 1626.68,1720.96 1626.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1626.68 1720.96 L1626.68 1720.96 L1626.96 1720.96 L1626.96 1720.96 L1626.68 1720.96 L1626.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1626.68,1720.96 1626.68,1720.96 1626.96,1720.96 1626.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1626.96 1720.96 L1626.96 1720.96 L1627.24 1720.96 L1627.24 1720.96 L1626.96 1720.96 L1626.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1626.96,1720.96 1626.96,1720.96 1627.24,1720.96 1626.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1627.24 1720.96 L1627.24 1720.96 L1627.53 1720.96 L1627.53 1720.96 L1627.24 1720.96 L1627.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1627.24,1720.96 1627.24,1720.96 1627.53,1720.96 1627.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1627.53 1720.96 L1627.53 1720.96 L1627.81 1720.96 L1627.81 1720.96 L1627.53 1720.96 L1627.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1627.53,1720.96 1627.53,1720.96 1627.81,1720.96 1627.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1627.81 1720.96 L1627.81 1720.96 L1628.09 1720.96 L1628.09 1720.96 L1627.81 1720.96 L1627.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1627.81,1720.96 1627.81,1720.96 1628.09,1720.96 1627.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1628.09 1720.96 L1628.09 1720.96 L1628.37 1720.96 L1628.37 1720.96 L1628.09 1720.96 L1628.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1628.09,1720.96 1628.09,1720.96 1628.37,1720.96 1628.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1628.37 1720.96 L1628.37 1720.96 L1628.65 1720.96 L1628.65 1720.96 L1628.37 1720.96 L1628.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1628.37,1720.96 1628.37,1720.96 1628.65,1720.96 1628.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1628.65 1720.96 L1628.65 1720.96 L1628.94 1720.96 L1628.94 1720.96 L1628.65 1720.96 L1628.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1628.65,1720.96 1628.65,1720.96 1628.94,1720.96 1628.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1628.94 1720.96 L1628.94 1720.96 L1629.22 1720.96 L1629.22 1720.96 L1628.94 1720.96 L1628.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1628.94,1720.96 1628.94,1720.96 1629.22,1720.96 1628.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1629.22 1720.96 L1629.22 1720.96 L1629.5 1720.96 L1629.5 1720.96 L1629.22 1720.96 L1629.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1629.22,1720.96 1629.22,1720.96 1629.5,1720.96 1629.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1629.5 1720.96 L1629.5 1720.96 L1629.78 1720.96 L1629.78 1720.96 L1629.5 1720.96 L1629.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1629.5,1720.96 1629.5,1720.96 1629.78,1720.96 1629.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1629.78 1720.96 L1629.78 1720.96 L1630.06 1720.96 L1630.06 1720.96 L1629.78 1720.96 L1629.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1629.78,1720.96 1629.78,1720.96 1630.06,1720.96 1629.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1630.06 1720.96 L1630.06 1720.96 L1630.34 1720.96 L1630.34 1720.96 L1630.06 1720.96 L1630.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1630.06,1720.96 1630.06,1720.96 1630.34,1720.96 1630.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1630.34 1720.96 L1630.34 1720.96 L1630.63 1720.96 L1630.63 1720.96 L1630.34 1720.96 L1630.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1630.34,1720.96 1630.34,1720.96 1630.63,1720.96 1630.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1630.63 1720.76 L1630.63 1720.96 L1630.91 1720.96 L1630.91 1720.76 L1630.63 1720.76 L1630.63 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1630.63,1720.76 1630.63,1720.96 1630.91,1720.96 1630.91,1720.76 1630.63,1720.76 "/>
<path clip-path="url(#clip322)" d="M1630.91 1720.96 L1630.91 1720.96 L1631.19 1720.96 L1631.19 1720.96 L1630.91 1720.96 L1630.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1630.91,1720.96 1630.91,1720.96 1631.19,1720.96 1630.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1631.19 1720.96 L1631.19 1720.96 L1631.47 1720.96 L1631.47 1720.96 L1631.19 1720.96 L1631.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1631.19,1720.96 1631.19,1720.96 1631.47,1720.96 1631.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1631.47 1720.96 L1631.47 1720.96 L1631.75 1720.96 L1631.75 1720.96 L1631.47 1720.96 L1631.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1631.47,1720.96 1631.47,1720.96 1631.75,1720.96 1631.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1631.75 1720.76 L1631.75 1720.96 L1632.03 1720.96 L1632.03 1720.76 L1631.75 1720.76 L1631.75 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1631.75,1720.76 1631.75,1720.96 1632.03,1720.96 1632.03,1720.76 1631.75,1720.76 "/>
<path clip-path="url(#clip322)" d="M1632.03 1720.96 L1632.03 1720.96 L1632.32 1720.96 L1632.32 1720.96 L1632.03 1720.96 L1632.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1632.03,1720.96 1632.03,1720.96 1632.32,1720.96 1632.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1632.32 1720.96 L1632.32 1720.96 L1632.6 1720.96 L1632.6 1720.96 L1632.32 1720.96 L1632.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1632.32,1720.96 1632.32,1720.96 1632.6,1720.96 1632.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1632.6 1720.96 L1632.6 1720.96 L1632.88 1720.96 L1632.88 1720.96 L1632.6 1720.96 L1632.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1632.6,1720.96 1632.6,1720.96 1632.88,1720.96 1632.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1632.88 1720.96 L1632.88 1720.96 L1633.16 1720.96 L1633.16 1720.96 L1632.88 1720.96 L1632.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1632.88,1720.96 1632.88,1720.96 1633.16,1720.96 1632.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1633.16 1720.96 L1633.16 1720.96 L1633.44 1720.96 L1633.44 1720.96 L1633.16 1720.96 L1633.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1633.16,1720.96 1633.16,1720.96 1633.44,1720.96 1633.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1633.44 1720.96 L1633.44 1720.96 L1633.72 1720.96 L1633.72 1720.96 L1633.44 1720.96 L1633.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1633.44,1720.96 1633.44,1720.96 1633.72,1720.96 1633.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1633.72 1720.96 L1633.72 1720.96 L1634.01 1720.96 L1634.01 1720.96 L1633.72 1720.96 L1633.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1633.72,1720.96 1633.72,1720.96 1634.01,1720.96 1633.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1634.01 1720.96 L1634.01 1720.96 L1634.29 1720.96 L1634.29 1720.96 L1634.01 1720.96 L1634.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1634.01,1720.96 1634.01,1720.96 1634.29,1720.96 1634.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1634.29 1720.96 L1634.29 1720.96 L1634.57 1720.96 L1634.57 1720.96 L1634.29 1720.96 L1634.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1634.29,1720.96 1634.29,1720.96 1634.57,1720.96 1634.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1634.57 1720.96 L1634.57 1720.96 L1634.85 1720.96 L1634.85 1720.96 L1634.57 1720.96 L1634.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1634.57,1720.96 1634.57,1720.96 1634.85,1720.96 1634.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1634.85 1720.96 L1634.85 1720.96 L1635.13 1720.96 L1635.13 1720.96 L1634.85 1720.96 L1634.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1634.85,1720.96 1634.85,1720.96 1635.13,1720.96 1634.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1635.13 1720.96 L1635.13 1720.96 L1635.41 1720.96 L1635.41 1720.96 L1635.13 1720.96 L1635.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1635.13,1720.96 1635.13,1720.96 1635.41,1720.96 1635.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1635.41 1720.96 L1635.41 1720.96 L1635.7 1720.96 L1635.7 1720.96 L1635.41 1720.96 L1635.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1635.41,1720.96 1635.41,1720.96 1635.7,1720.96 1635.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1635.7 1720.96 L1635.7 1720.96 L1635.98 1720.96 L1635.98 1720.96 L1635.7 1720.96 L1635.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1635.7,1720.96 1635.7,1720.96 1635.98,1720.96 1635.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1635.98 1720.96 L1635.98 1720.96 L1636.26 1720.96 L1636.26 1720.96 L1635.98 1720.96 L1635.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1635.98,1720.96 1635.98,1720.96 1636.26,1720.96 1635.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1636.26 1720.96 L1636.26 1720.96 L1636.54 1720.96 L1636.54 1720.96 L1636.26 1720.96 L1636.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1636.26,1720.96 1636.26,1720.96 1636.54,1720.96 1636.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1636.54 1720.96 L1636.54 1720.96 L1636.82 1720.96 L1636.82 1720.96 L1636.54 1720.96 L1636.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1636.54,1720.96 1636.54,1720.96 1636.82,1720.96 1636.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1636.82 1720.96 L1636.82 1720.96 L1637.11 1720.96 L1637.11 1720.96 L1636.82 1720.96 L1636.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1636.82,1720.96 1636.82,1720.96 1637.11,1720.96 1636.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1637.11 1720.96 L1637.11 1720.96 L1637.39 1720.96 L1637.39 1720.96 L1637.11 1720.96 L1637.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1637.11,1720.96 1637.11,1720.96 1637.39,1720.96 1637.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1637.39 1720.96 L1637.39 1720.96 L1637.67 1720.96 L1637.67 1720.96 L1637.39 1720.96 L1637.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1637.39,1720.96 1637.39,1720.96 1637.67,1720.96 1637.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1637.67 1720.96 L1637.67 1720.96 L1637.95 1720.96 L1637.95 1720.96 L1637.67 1720.96 L1637.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1637.67,1720.96 1637.67,1720.96 1637.95,1720.96 1637.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1637.95 1720.96 L1637.95 1720.96 L1638.23 1720.96 L1638.23 1720.96 L1637.95 1720.96 L1637.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1637.95,1720.96 1637.95,1720.96 1638.23,1720.96 1637.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1638.23 1720.96 L1638.23 1720.96 L1638.51 1720.96 L1638.51 1720.96 L1638.23 1720.96 L1638.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1638.23,1720.96 1638.23,1720.96 1638.51,1720.96 1638.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1638.51 1720.96 L1638.51 1720.96 L1638.8 1720.96 L1638.8 1720.96 L1638.51 1720.96 L1638.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1638.51,1720.96 1638.51,1720.96 1638.8,1720.96 1638.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1638.8 1720.96 L1638.8 1720.96 L1639.08 1720.96 L1639.08 1720.96 L1638.8 1720.96 L1638.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1638.8,1720.96 1638.8,1720.96 1639.08,1720.96 1638.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1639.08 1720.96 L1639.08 1720.96 L1639.36 1720.96 L1639.36 1720.96 L1639.08 1720.96 L1639.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1639.08,1720.96 1639.08,1720.96 1639.36,1720.96 1639.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1639.36 1720.96 L1639.36 1720.96 L1639.64 1720.96 L1639.64 1720.96 L1639.36 1720.96 L1639.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1639.36,1720.96 1639.36,1720.96 1639.64,1720.96 1639.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1639.64 1720.96 L1639.64 1720.96 L1639.92 1720.96 L1639.92 1720.96 L1639.64 1720.96 L1639.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1639.64,1720.96 1639.64,1720.96 1639.92,1720.96 1639.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1639.92 1720.96 L1639.92 1720.96 L1640.2 1720.96 L1640.2 1720.96 L1639.92 1720.96 L1639.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1639.92,1720.96 1639.92,1720.96 1640.2,1720.96 1639.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1640.2 1720.96 L1640.2 1720.96 L1640.49 1720.96 L1640.49 1720.96 L1640.2 1720.96 L1640.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1640.2,1720.96 1640.2,1720.96 1640.49,1720.96 1640.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1640.49 1720.96 L1640.49 1720.96 L1640.77 1720.96 L1640.77 1720.96 L1640.49 1720.96 L1640.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1640.49,1720.96 1640.49,1720.96 1640.77,1720.96 1640.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1640.77 1720.96 L1640.77 1720.96 L1641.05 1720.96 L1641.05 1720.96 L1640.77 1720.96 L1640.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1640.77,1720.96 1640.77,1720.96 1641.05,1720.96 1640.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1641.05 1720.96 L1641.05 1720.96 L1641.33 1720.96 L1641.33 1720.96 L1641.05 1720.96 L1641.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1641.05,1720.96 1641.05,1720.96 1641.33,1720.96 1641.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1641.33 1720.96 L1641.33 1720.96 L1641.61 1720.96 L1641.61 1720.96 L1641.33 1720.96 L1641.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1641.33,1720.96 1641.33,1720.96 1641.61,1720.96 1641.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1641.61 1720.96 L1641.61 1720.96 L1641.89 1720.96 L1641.89 1720.96 L1641.61 1720.96 L1641.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1641.61,1720.96 1641.61,1720.96 1641.89,1720.96 1641.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1641.89 1720.96 L1641.89 1720.96 L1642.18 1720.96 L1642.18 1720.96 L1641.89 1720.96 L1641.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1641.89,1720.96 1641.89,1720.96 1642.18,1720.96 1641.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1642.18 1720.96 L1642.18 1720.96 L1642.46 1720.96 L1642.46 1720.96 L1642.18 1720.96 L1642.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1642.18,1720.96 1642.18,1720.96 1642.46,1720.96 1642.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1642.46 1720.96 L1642.46 1720.96 L1642.74 1720.96 L1642.74 1720.96 L1642.46 1720.96 L1642.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1642.46,1720.96 1642.46,1720.96 1642.74,1720.96 1642.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1642.74 1720.96 L1642.74 1720.96 L1643.02 1720.96 L1643.02 1720.96 L1642.74 1720.96 L1642.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1642.74,1720.96 1642.74,1720.96 1643.02,1720.96 1642.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1643.02 1720.96 L1643.02 1720.96 L1643.3 1720.96 L1643.3 1720.96 L1643.02 1720.96 L1643.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1643.02,1720.96 1643.02,1720.96 1643.3,1720.96 1643.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1643.3 1720.96 L1643.3 1720.96 L1643.58 1720.96 L1643.58 1720.96 L1643.3 1720.96 L1643.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1643.3,1720.96 1643.3,1720.96 1643.58,1720.96 1643.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1643.58 1720.96 L1643.58 1720.96 L1643.87 1720.96 L1643.87 1720.96 L1643.58 1720.96 L1643.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1643.58,1720.96 1643.58,1720.96 1643.87,1720.96 1643.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1643.87 1720.96 L1643.87 1720.96 L1644.15 1720.96 L1644.15 1720.96 L1643.87 1720.96 L1643.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1643.87,1720.96 1643.87,1720.96 1644.15,1720.96 1643.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1644.15 1720.96 L1644.15 1720.96 L1644.43 1720.96 L1644.43 1720.96 L1644.15 1720.96 L1644.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1644.15,1720.96 1644.15,1720.96 1644.43,1720.96 1644.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1644.43 1720.96 L1644.43 1720.96 L1644.71 1720.96 L1644.71 1720.96 L1644.43 1720.96 L1644.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1644.43,1720.96 1644.43,1720.96 1644.71,1720.96 1644.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1644.71 1720.96 L1644.71 1720.96 L1644.99 1720.96 L1644.99 1720.96 L1644.71 1720.96 L1644.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1644.71,1720.96 1644.71,1720.96 1644.99,1720.96 1644.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1644.99 1720.96 L1644.99 1720.96 L1645.28 1720.96 L1645.28 1720.96 L1644.99 1720.96 L1644.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1644.99,1720.96 1644.99,1720.96 1645.28,1720.96 1644.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1645.28 1720.96 L1645.28 1720.96 L1645.56 1720.96 L1645.56 1720.96 L1645.28 1720.96 L1645.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1645.28,1720.96 1645.28,1720.96 1645.56,1720.96 1645.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1645.56 1720.96 L1645.56 1720.96 L1645.84 1720.96 L1645.84 1720.96 L1645.56 1720.96 L1645.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1645.56,1720.96 1645.56,1720.96 1645.84,1720.96 1645.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1645.84 1720.96 L1645.84 1720.96 L1646.12 1720.96 L1646.12 1720.96 L1645.84 1720.96 L1645.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1645.84,1720.96 1645.84,1720.96 1646.12,1720.96 1645.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1646.12 1720.96 L1646.12 1720.96 L1646.4 1720.96 L1646.4 1720.96 L1646.12 1720.96 L1646.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1646.12,1720.96 1646.12,1720.96 1646.4,1720.96 1646.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1646.4 1720.96 L1646.4 1720.96 L1646.68 1720.96 L1646.68 1720.96 L1646.4 1720.96 L1646.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1646.4,1720.96 1646.4,1720.96 1646.68,1720.96 1646.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1646.68 1720.96 L1646.68 1720.96 L1646.97 1720.96 L1646.97 1720.96 L1646.68 1720.96 L1646.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1646.68,1720.96 1646.68,1720.96 1646.97,1720.96 1646.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1646.97 1720.96 L1646.97 1720.96 L1647.25 1720.96 L1647.25 1720.96 L1646.97 1720.96 L1646.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1646.97,1720.96 1646.97,1720.96 1647.25,1720.96 1646.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1647.25 1720.96 L1647.25 1720.96 L1647.53 1720.96 L1647.53 1720.96 L1647.25 1720.96 L1647.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1647.25,1720.96 1647.25,1720.96 1647.53,1720.96 1647.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1647.53 1720.96 L1647.53 1720.96 L1647.81 1720.96 L1647.81 1720.96 L1647.53 1720.96 L1647.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1647.53,1720.96 1647.53,1720.96 1647.81,1720.96 1647.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1647.81 1720.96 L1647.81 1720.96 L1648.09 1720.96 L1648.09 1720.96 L1647.81 1720.96 L1647.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1647.81,1720.96 1647.81,1720.96 1648.09,1720.96 1647.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1648.09 1720.96 L1648.09 1720.96 L1648.37 1720.96 L1648.37 1720.96 L1648.09 1720.96 L1648.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1648.09,1720.96 1648.09,1720.96 1648.37,1720.96 1648.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1648.37 1720.96 L1648.37 1720.96 L1648.66 1720.96 L1648.66 1720.96 L1648.37 1720.96 L1648.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1648.37,1720.96 1648.37,1720.96 1648.66,1720.96 1648.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1648.66 1720.96 L1648.66 1720.96 L1648.94 1720.96 L1648.94 1720.96 L1648.66 1720.96 L1648.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1648.66,1720.96 1648.66,1720.96 1648.94,1720.96 1648.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1648.94 1720.96 L1648.94 1720.96 L1649.22 1720.96 L1649.22 1720.96 L1648.94 1720.96 L1648.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1648.94,1720.96 1648.94,1720.96 1649.22,1720.96 1648.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1649.22 1720.96 L1649.22 1720.96 L1649.5 1720.96 L1649.5 1720.96 L1649.22 1720.96 L1649.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1649.22,1720.96 1649.22,1720.96 1649.5,1720.96 1649.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1649.5 1720.96 L1649.5 1720.96 L1649.78 1720.96 L1649.78 1720.96 L1649.5 1720.96 L1649.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1649.5,1720.96 1649.5,1720.96 1649.78,1720.96 1649.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1649.78 1720.96 L1649.78 1720.96 L1650.06 1720.96 L1650.06 1720.96 L1649.78 1720.96 L1649.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1649.78,1720.96 1649.78,1720.96 1650.06,1720.96 1649.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1650.06 1720.96 L1650.06 1720.96 L1650.35 1720.96 L1650.35 1720.96 L1650.06 1720.96 L1650.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1650.06,1720.96 1650.06,1720.96 1650.35,1720.96 1650.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1650.35 1720.96 L1650.35 1720.96 L1650.63 1720.96 L1650.63 1720.96 L1650.35 1720.96 L1650.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1650.35,1720.96 1650.35,1720.96 1650.63,1720.96 1650.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1650.63 1720.96 L1650.63 1720.96 L1650.91 1720.96 L1650.91 1720.96 L1650.63 1720.96 L1650.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1650.63,1720.96 1650.63,1720.96 1650.91,1720.96 1650.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1650.91 1720.96 L1650.91 1720.96 L1651.19 1720.96 L1651.19 1720.96 L1650.91 1720.96 L1650.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1650.91,1720.96 1650.91,1720.96 1651.19,1720.96 1650.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1651.19 1720.96 L1651.19 1720.96 L1651.47 1720.96 L1651.47 1720.96 L1651.19 1720.96 L1651.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1651.19,1720.96 1651.19,1720.96 1651.47,1720.96 1651.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1651.47 1720.96 L1651.47 1720.96 L1651.76 1720.96 L1651.76 1720.96 L1651.47 1720.96 L1651.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1651.47,1720.96 1651.47,1720.96 1651.76,1720.96 1651.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1651.76 1720.96 L1651.76 1720.96 L1652.04 1720.96 L1652.04 1720.96 L1651.76 1720.96 L1651.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1651.76,1720.96 1651.76,1720.96 1652.04,1720.96 1651.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1652.04 1720.96 L1652.04 1720.96 L1652.32 1720.96 L1652.32 1720.96 L1652.04 1720.96 L1652.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1652.04,1720.96 1652.04,1720.96 1652.32,1720.96 1652.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1652.32 1720.96 L1652.32 1720.96 L1652.6 1720.96 L1652.6 1720.96 L1652.32 1720.96 L1652.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1652.32,1720.96 1652.32,1720.96 1652.6,1720.96 1652.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1652.6 1720.76 L1652.6 1720.96 L1652.88 1720.96 L1652.88 1720.76 L1652.6 1720.76 L1652.6 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1652.6,1720.76 1652.6,1720.96 1652.88,1720.96 1652.88,1720.76 1652.6,1720.76 "/>
<path clip-path="url(#clip322)" d="M1652.88 1720.96 L1652.88 1720.96 L1653.16 1720.96 L1653.16 1720.96 L1652.88 1720.96 L1652.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1652.88,1720.96 1652.88,1720.96 1653.16,1720.96 1652.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1653.16 1720.96 L1653.16 1720.96 L1653.45 1720.96 L1653.45 1720.96 L1653.16 1720.96 L1653.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1653.16,1720.96 1653.16,1720.96 1653.45,1720.96 1653.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1653.45 1720.96 L1653.45 1720.96 L1653.73 1720.96 L1653.73 1720.96 L1653.45 1720.96 L1653.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1653.45,1720.96 1653.45,1720.96 1653.73,1720.96 1653.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1653.73 1720.96 L1653.73 1720.96 L1654.01 1720.96 L1654.01 1720.96 L1653.73 1720.96 L1653.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1653.73,1720.96 1653.73,1720.96 1654.01,1720.96 1653.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1654.01 1720.96 L1654.01 1720.96 L1654.29 1720.96 L1654.29 1720.96 L1654.01 1720.96 L1654.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1654.01,1720.96 1654.01,1720.96 1654.29,1720.96 1654.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1654.29 1720.96 L1654.29 1720.96 L1654.57 1720.96 L1654.57 1720.96 L1654.29 1720.96 L1654.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1654.29,1720.96 1654.29,1720.96 1654.57,1720.96 1654.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1654.57 1720.96 L1654.57 1720.96 L1654.85 1720.96 L1654.85 1720.96 L1654.57 1720.96 L1654.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1654.57,1720.96 1654.57,1720.96 1654.85,1720.96 1654.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1654.85 1720.96 L1654.85 1720.96 L1655.14 1720.96 L1655.14 1720.96 L1654.85 1720.96 L1654.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1654.85,1720.96 1654.85,1720.96 1655.14,1720.96 1654.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1655.14 1720.96 L1655.14 1720.96 L1655.42 1720.96 L1655.42 1720.96 L1655.14 1720.96 L1655.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1655.14,1720.96 1655.14,1720.96 1655.42,1720.96 1655.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1655.42 1720.96 L1655.42 1720.96 L1655.7 1720.96 L1655.7 1720.96 L1655.42 1720.96 L1655.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1655.42,1720.96 1655.42,1720.96 1655.7,1720.96 1655.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1655.7 1720.96 L1655.7 1720.96 L1655.98 1720.96 L1655.98 1720.96 L1655.7 1720.96 L1655.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1655.7,1720.96 1655.7,1720.96 1655.98,1720.96 1655.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1655.98 1720.96 L1655.98 1720.96 L1656.26 1720.96 L1656.26 1720.96 L1655.98 1720.96 L1655.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1655.98,1720.96 1655.98,1720.96 1656.26,1720.96 1655.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1656.26 1720.96 L1656.26 1720.96 L1656.54 1720.96 L1656.54 1720.96 L1656.26 1720.96 L1656.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1656.26,1720.96 1656.26,1720.96 1656.54,1720.96 1656.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1656.54 1720.76 L1656.54 1720.96 L1656.83 1720.96 L1656.83 1720.76 L1656.54 1720.76 L1656.54 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1656.54,1720.76 1656.54,1720.96 1656.83,1720.96 1656.83,1720.76 1656.54,1720.76 "/>
<path clip-path="url(#clip322)" d="M1656.83 1720.96 L1656.83 1720.96 L1657.11 1720.96 L1657.11 1720.96 L1656.83 1720.96 L1656.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1656.83,1720.96 1656.83,1720.96 1657.11,1720.96 1656.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1657.11 1720.96 L1657.11 1720.96 L1657.39 1720.96 L1657.39 1720.96 L1657.11 1720.96 L1657.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1657.11,1720.96 1657.11,1720.96 1657.39,1720.96 1657.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1657.39 1720.96 L1657.39 1720.96 L1657.67 1720.96 L1657.67 1720.96 L1657.39 1720.96 L1657.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1657.39,1720.96 1657.39,1720.96 1657.67,1720.96 1657.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1657.67 1720.96 L1657.67 1720.96 L1657.95 1720.96 L1657.95 1720.96 L1657.67 1720.96 L1657.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1657.67,1720.96 1657.67,1720.96 1657.95,1720.96 1657.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1657.95 1720.96 L1657.95 1720.96 L1658.23 1720.96 L1658.23 1720.96 L1657.95 1720.96 L1657.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1657.95,1720.96 1657.95,1720.96 1658.23,1720.96 1657.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1658.23 1720.96 L1658.23 1720.96 L1658.52 1720.96 L1658.52 1720.96 L1658.23 1720.96 L1658.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1658.23,1720.96 1658.23,1720.96 1658.52,1720.96 1658.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1658.52 1720.96 L1658.52 1720.96 L1658.8 1720.96 L1658.8 1720.96 L1658.52 1720.96 L1658.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1658.52,1720.96 1658.52,1720.96 1658.8,1720.96 1658.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1658.8 1720.96 L1658.8 1720.96 L1659.08 1720.96 L1659.08 1720.96 L1658.8 1720.96 L1658.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1658.8,1720.96 1658.8,1720.96 1659.08,1720.96 1658.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1659.08 1720.96 L1659.08 1720.96 L1659.36 1720.96 L1659.36 1720.96 L1659.08 1720.96 L1659.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1659.08,1720.96 1659.08,1720.96 1659.36,1720.96 1659.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1659.36 1720.96 L1659.36 1720.96 L1659.64 1720.96 L1659.64 1720.96 L1659.36 1720.96 L1659.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1659.36,1720.96 1659.36,1720.96 1659.64,1720.96 1659.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1659.64 1720.96 L1659.64 1720.96 L1659.93 1720.96 L1659.93 1720.96 L1659.64 1720.96 L1659.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1659.64,1720.96 1659.64,1720.96 1659.93,1720.96 1659.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1659.93 1720.96 L1659.93 1720.96 L1660.21 1720.96 L1660.21 1720.96 L1659.93 1720.96 L1659.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1659.93,1720.96 1659.93,1720.96 1660.21,1720.96 1659.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1660.21 1720.96 L1660.21 1720.96 L1660.49 1720.96 L1660.49 1720.96 L1660.21 1720.96 L1660.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1660.21,1720.96 1660.21,1720.96 1660.49,1720.96 1660.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1660.49 1720.76 L1660.49 1720.96 L1660.77 1720.96 L1660.77 1720.76 L1660.49 1720.76 L1660.49 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1660.49,1720.76 1660.49,1720.96 1660.77,1720.96 1660.77,1720.76 1660.49,1720.76 "/>
<path clip-path="url(#clip322)" d="M1660.77 1720.96 L1660.77 1720.96 L1661.05 1720.96 L1661.05 1720.96 L1660.77 1720.96 L1660.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1660.77,1720.96 1660.77,1720.96 1661.05,1720.96 1660.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1661.05 1720.96 L1661.05 1720.96 L1661.33 1720.96 L1661.33 1720.96 L1661.05 1720.96 L1661.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1661.05,1720.96 1661.05,1720.96 1661.33,1720.96 1661.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1661.33 1720.96 L1661.33 1720.96 L1661.62 1720.96 L1661.62 1720.96 L1661.33 1720.96 L1661.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1661.33,1720.96 1661.33,1720.96 1661.62,1720.96 1661.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1661.62 1720.96 L1661.62 1720.96 L1661.9 1720.96 L1661.9 1720.96 L1661.62 1720.96 L1661.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1661.62,1720.96 1661.62,1720.96 1661.9,1720.96 1661.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1661.9 1720.96 L1661.9 1720.96 L1662.18 1720.96 L1662.18 1720.96 L1661.9 1720.96 L1661.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1661.9,1720.96 1661.9,1720.96 1662.18,1720.96 1661.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1662.18 1720.96 L1662.18 1720.96 L1662.46 1720.96 L1662.46 1720.96 L1662.18 1720.96 L1662.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1662.18,1720.96 1662.18,1720.96 1662.46,1720.96 1662.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1662.46 1720.96 L1662.46 1720.96 L1662.74 1720.96 L1662.74 1720.96 L1662.46 1720.96 L1662.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1662.46,1720.96 1662.46,1720.96 1662.74,1720.96 1662.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1662.74 1720.96 L1662.74 1720.96 L1663.02 1720.96 L1663.02 1720.96 L1662.74 1720.96 L1662.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1662.74,1720.96 1662.74,1720.96 1663.02,1720.96 1662.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1663.02 1720.96 L1663.02 1720.96 L1663.31 1720.96 L1663.31 1720.96 L1663.02 1720.96 L1663.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1663.02,1720.96 1663.02,1720.96 1663.31,1720.96 1663.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1663.31 1720.96 L1663.31 1720.96 L1663.59 1720.96 L1663.59 1720.96 L1663.31 1720.96 L1663.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1663.31,1720.96 1663.31,1720.96 1663.59,1720.96 1663.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1663.59 1720.96 L1663.59 1720.96 L1663.87 1720.96 L1663.87 1720.96 L1663.59 1720.96 L1663.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1663.59,1720.96 1663.59,1720.96 1663.87,1720.96 1663.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1663.87 1720.96 L1663.87 1720.96 L1664.15 1720.96 L1664.15 1720.96 L1663.87 1720.96 L1663.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1663.87,1720.96 1663.87,1720.96 1664.15,1720.96 1663.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1664.15 1720.96 L1664.15 1720.96 L1664.43 1720.96 L1664.43 1720.96 L1664.15 1720.96 L1664.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1664.15,1720.96 1664.15,1720.96 1664.43,1720.96 1664.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1664.43 1720.96 L1664.43 1720.96 L1664.71 1720.96 L1664.71 1720.96 L1664.43 1720.96 L1664.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1664.43,1720.96 1664.43,1720.96 1664.71,1720.96 1664.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1664.71 1720.96 L1664.71 1720.96 L1665 1720.96 L1665 1720.96 L1664.71 1720.96 L1664.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1664.71,1720.96 1664.71,1720.96 1665,1720.96 1664.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1665 1720.96 L1665 1720.96 L1665.28 1720.96 L1665.28 1720.96 L1665 1720.96 L1665 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1665,1720.96 1665,1720.96 1665.28,1720.96 1665,1720.96 "/>
<path clip-path="url(#clip322)" d="M1665.28 1720.96 L1665.28 1720.96 L1665.56 1720.96 L1665.56 1720.96 L1665.28 1720.96 L1665.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1665.28,1720.96 1665.28,1720.96 1665.56,1720.96 1665.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1665.56 1720.96 L1665.56 1720.96 L1665.84 1720.96 L1665.84 1720.96 L1665.56 1720.96 L1665.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1665.56,1720.96 1665.56,1720.96 1665.84,1720.96 1665.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1665.84 1720.96 L1665.84 1720.96 L1666.12 1720.96 L1666.12 1720.96 L1665.84 1720.96 L1665.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1665.84,1720.96 1665.84,1720.96 1666.12,1720.96 1665.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1666.12 1720.96 L1666.12 1720.96 L1666.4 1720.96 L1666.4 1720.96 L1666.12 1720.96 L1666.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1666.12,1720.96 1666.12,1720.96 1666.4,1720.96 1666.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1666.4 1720.96 L1666.4 1720.96 L1666.69 1720.96 L1666.69 1720.96 L1666.4 1720.96 L1666.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1666.4,1720.96 1666.4,1720.96 1666.69,1720.96 1666.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1666.69 1720.76 L1666.69 1720.96 L1666.97 1720.96 L1666.97 1720.76 L1666.69 1720.76 L1666.69 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1666.69,1720.76 1666.69,1720.96 1666.97,1720.96 1666.97,1720.76 1666.69,1720.76 "/>
<path clip-path="url(#clip322)" d="M1666.97 1720.96 L1666.97 1720.96 L1667.25 1720.96 L1667.25 1720.96 L1666.97 1720.96 L1666.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1666.97,1720.96 1666.97,1720.96 1667.25,1720.96 1666.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1667.25 1720.96 L1667.25 1720.96 L1667.53 1720.96 L1667.53 1720.96 L1667.25 1720.96 L1667.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1667.25,1720.96 1667.25,1720.96 1667.53,1720.96 1667.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1667.53 1720.96 L1667.53 1720.96 L1667.81 1720.96 L1667.81 1720.96 L1667.53 1720.96 L1667.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1667.53,1720.96 1667.53,1720.96 1667.81,1720.96 1667.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1667.81 1720.96 L1667.81 1720.96 L1668.1 1720.96 L1668.1 1720.96 L1667.81 1720.96 L1667.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1667.81,1720.96 1667.81,1720.96 1668.1,1720.96 1667.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1668.1 1720.96 L1668.1 1720.96 L1668.38 1720.96 L1668.38 1720.96 L1668.1 1720.96 L1668.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1668.1,1720.96 1668.1,1720.96 1668.38,1720.96 1668.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1668.38 1720.96 L1668.38 1720.96 L1668.66 1720.96 L1668.66 1720.96 L1668.38 1720.96 L1668.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1668.38,1720.96 1668.38,1720.96 1668.66,1720.96 1668.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1668.66 1720.96 L1668.66 1720.96 L1668.94 1720.96 L1668.94 1720.96 L1668.66 1720.96 L1668.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1668.66,1720.96 1668.66,1720.96 1668.94,1720.96 1668.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1668.94 1720.96 L1668.94 1720.96 L1669.22 1720.96 L1669.22 1720.96 L1668.94 1720.96 L1668.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1668.94,1720.96 1668.94,1720.96 1669.22,1720.96 1668.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1669.22 1720.96 L1669.22 1720.96 L1669.5 1720.96 L1669.5 1720.96 L1669.22 1720.96 L1669.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1669.22,1720.96 1669.22,1720.96 1669.5,1720.96 1669.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1669.5 1720.96 L1669.5 1720.96 L1669.79 1720.96 L1669.79 1720.96 L1669.5 1720.96 L1669.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1669.5,1720.96 1669.5,1720.96 1669.79,1720.96 1669.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1669.79 1720.96 L1669.79 1720.96 L1670.07 1720.96 L1670.07 1720.96 L1669.79 1720.96 L1669.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1669.79,1720.96 1669.79,1720.96 1670.07,1720.96 1669.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1670.07 1720.96 L1670.07 1720.96 L1670.35 1720.96 L1670.35 1720.96 L1670.07 1720.96 L1670.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1670.07,1720.96 1670.07,1720.96 1670.35,1720.96 1670.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1670.35 1720.96 L1670.35 1720.96 L1670.63 1720.96 L1670.63 1720.96 L1670.35 1720.96 L1670.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1670.35,1720.96 1670.35,1720.96 1670.63,1720.96 1670.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1670.63 1720.96 L1670.63 1720.96 L1670.91 1720.96 L1670.91 1720.96 L1670.63 1720.96 L1670.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1670.63,1720.96 1670.63,1720.96 1670.91,1720.96 1670.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1670.91 1720.96 L1670.91 1720.96 L1671.19 1720.96 L1671.19 1720.96 L1670.91 1720.96 L1670.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1670.91,1720.96 1670.91,1720.96 1671.19,1720.96 1670.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1671.19 1720.96 L1671.19 1720.96 L1671.48 1720.96 L1671.48 1720.96 L1671.19 1720.96 L1671.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1671.19,1720.96 1671.19,1720.96 1671.48,1720.96 1671.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1671.48 1720.96 L1671.48 1720.96 L1671.76 1720.96 L1671.76 1720.96 L1671.48 1720.96 L1671.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1671.48,1720.96 1671.48,1720.96 1671.76,1720.96 1671.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1671.76 1720.96 L1671.76 1720.96 L1672.04 1720.96 L1672.04 1720.96 L1671.76 1720.96 L1671.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1671.76,1720.96 1671.76,1720.96 1672.04,1720.96 1671.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1672.04 1720.96 L1672.04 1720.96 L1672.32 1720.96 L1672.32 1720.96 L1672.04 1720.96 L1672.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1672.04,1720.96 1672.04,1720.96 1672.32,1720.96 1672.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1672.32 1720.96 L1672.32 1720.96 L1672.6 1720.96 L1672.6 1720.96 L1672.32 1720.96 L1672.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1672.32,1720.96 1672.32,1720.96 1672.6,1720.96 1672.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1672.6 1720.96 L1672.6 1720.96 L1672.88 1720.96 L1672.88 1720.96 L1672.6 1720.96 L1672.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1672.6,1720.96 1672.6,1720.96 1672.88,1720.96 1672.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1672.88 1720.96 L1672.88 1720.96 L1673.17 1720.96 L1673.17 1720.96 L1672.88 1720.96 L1672.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1672.88,1720.96 1672.88,1720.96 1673.17,1720.96 1672.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1673.17 1720.96 L1673.17 1720.96 L1673.45 1720.96 L1673.45 1720.96 L1673.17 1720.96 L1673.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1673.17,1720.96 1673.17,1720.96 1673.45,1720.96 1673.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1673.45 1720.96 L1673.45 1720.96 L1673.73 1720.96 L1673.73 1720.96 L1673.45 1720.96 L1673.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1673.45,1720.96 1673.45,1720.96 1673.73,1720.96 1673.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1673.73 1720.96 L1673.73 1720.96 L1674.01 1720.96 L1674.01 1720.96 L1673.73 1720.96 L1673.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1673.73,1720.96 1673.73,1720.96 1674.01,1720.96 1673.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1674.01 1720.96 L1674.01 1720.96 L1674.29 1720.96 L1674.29 1720.96 L1674.01 1720.96 L1674.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1674.01,1720.96 1674.01,1720.96 1674.29,1720.96 1674.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1674.29 1720.96 L1674.29 1720.96 L1674.57 1720.96 L1674.57 1720.96 L1674.29 1720.96 L1674.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1674.29,1720.96 1674.29,1720.96 1674.57,1720.96 1674.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1674.57 1720.96 L1674.57 1720.96 L1674.86 1720.96 L1674.86 1720.96 L1674.57 1720.96 L1674.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1674.57,1720.96 1674.57,1720.96 1674.86,1720.96 1674.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1674.86 1720.96 L1674.86 1720.96 L1675.14 1720.96 L1675.14 1720.96 L1674.86 1720.96 L1674.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1674.86,1720.96 1674.86,1720.96 1675.14,1720.96 1674.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1675.14 1720.96 L1675.14 1720.96 L1675.42 1720.96 L1675.42 1720.96 L1675.14 1720.96 L1675.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1675.14,1720.96 1675.14,1720.96 1675.42,1720.96 1675.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1675.42 1720.96 L1675.42 1720.96 L1675.7 1720.96 L1675.7 1720.96 L1675.42 1720.96 L1675.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1675.42,1720.96 1675.42,1720.96 1675.7,1720.96 1675.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1675.7 1720.96 L1675.7 1720.96 L1675.98 1720.96 L1675.98 1720.96 L1675.7 1720.96 L1675.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1675.7,1720.96 1675.7,1720.96 1675.98,1720.96 1675.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1675.98 1720.96 L1675.98 1720.96 L1676.27 1720.96 L1676.27 1720.96 L1675.98 1720.96 L1675.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1675.98,1720.96 1675.98,1720.96 1676.27,1720.96 1675.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1676.27 1720.96 L1676.27 1720.96 L1676.55 1720.96 L1676.55 1720.96 L1676.27 1720.96 L1676.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1676.27,1720.96 1676.27,1720.96 1676.55,1720.96 1676.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1676.55 1720.96 L1676.55 1720.96 L1676.83 1720.96 L1676.83 1720.96 L1676.55 1720.96 L1676.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1676.55,1720.96 1676.55,1720.96 1676.83,1720.96 1676.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1676.83 1720.96 L1676.83 1720.96 L1677.11 1720.96 L1677.11 1720.96 L1676.83 1720.96 L1676.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1676.83,1720.96 1676.83,1720.96 1677.11,1720.96 1676.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1677.11 1720.96 L1677.11 1720.96 L1677.39 1720.96 L1677.39 1720.96 L1677.11 1720.96 L1677.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1677.11,1720.96 1677.11,1720.96 1677.39,1720.96 1677.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1677.39 1720.96 L1677.39 1720.96 L1677.67 1720.96 L1677.67 1720.96 L1677.39 1720.96 L1677.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1677.39,1720.96 1677.39,1720.96 1677.67,1720.96 1677.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1677.67 1720.96 L1677.67 1720.96 L1677.96 1720.96 L1677.96 1720.96 L1677.67 1720.96 L1677.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1677.67,1720.96 1677.67,1720.96 1677.96,1720.96 1677.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1677.96 1720.96 L1677.96 1720.96 L1678.24 1720.96 L1678.24 1720.96 L1677.96 1720.96 L1677.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1677.96,1720.96 1677.96,1720.96 1678.24,1720.96 1677.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1678.24 1720.96 L1678.24 1720.96 L1678.52 1720.96 L1678.52 1720.96 L1678.24 1720.96 L1678.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1678.24,1720.96 1678.24,1720.96 1678.52,1720.96 1678.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1678.52 1720.96 L1678.52 1720.96 L1678.8 1720.96 L1678.8 1720.96 L1678.52 1720.96 L1678.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1678.52,1720.96 1678.52,1720.96 1678.8,1720.96 1678.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1678.8 1720.96 L1678.8 1720.96 L1679.08 1720.96 L1679.08 1720.96 L1678.8 1720.96 L1678.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1678.8,1720.96 1678.8,1720.96 1679.08,1720.96 1678.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1679.08 1720.96 L1679.08 1720.96 L1679.36 1720.96 L1679.36 1720.96 L1679.08 1720.96 L1679.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1679.08,1720.96 1679.08,1720.96 1679.36,1720.96 1679.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1679.36 1720.96 L1679.36 1720.96 L1679.65 1720.96 L1679.65 1720.96 L1679.36 1720.96 L1679.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1679.36,1720.96 1679.36,1720.96 1679.65,1720.96 1679.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1679.65 1720.96 L1679.65 1720.96 L1679.93 1720.96 L1679.93 1720.96 L1679.65 1720.96 L1679.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1679.65,1720.96 1679.65,1720.96 1679.93,1720.96 1679.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1679.93 1720.96 L1679.93 1720.96 L1680.21 1720.96 L1680.21 1720.96 L1679.93 1720.96 L1679.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1679.93,1720.96 1679.93,1720.96 1680.21,1720.96 1679.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1680.21 1720.96 L1680.21 1720.96 L1680.49 1720.96 L1680.49 1720.96 L1680.21 1720.96 L1680.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1680.21,1720.96 1680.21,1720.96 1680.49,1720.96 1680.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1680.49 1720.96 L1680.49 1720.96 L1680.77 1720.96 L1680.77 1720.96 L1680.49 1720.96 L1680.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1680.49,1720.96 1680.49,1720.96 1680.77,1720.96 1680.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1680.77 1720.96 L1680.77 1720.96 L1681.05 1720.96 L1681.05 1720.96 L1680.77 1720.96 L1680.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1680.77,1720.96 1680.77,1720.96 1681.05,1720.96 1680.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1681.05 1720.96 L1681.05 1720.96 L1681.34 1720.96 L1681.34 1720.96 L1681.05 1720.96 L1681.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1681.05,1720.96 1681.05,1720.96 1681.34,1720.96 1681.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1681.34 1720.96 L1681.34 1720.96 L1681.62 1720.96 L1681.62 1720.96 L1681.34 1720.96 L1681.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1681.34,1720.96 1681.34,1720.96 1681.62,1720.96 1681.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1681.62 1720.96 L1681.62 1720.96 L1681.9 1720.96 L1681.9 1720.96 L1681.62 1720.96 L1681.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1681.62,1720.96 1681.62,1720.96 1681.9,1720.96 1681.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1681.9 1720.96 L1681.9 1720.96 L1682.18 1720.96 L1682.18 1720.96 L1681.9 1720.96 L1681.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1681.9,1720.96 1681.9,1720.96 1682.18,1720.96 1681.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1682.18 1720.96 L1682.18 1720.96 L1682.46 1720.96 L1682.46 1720.96 L1682.18 1720.96 L1682.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1682.18,1720.96 1682.18,1720.96 1682.46,1720.96 1682.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1682.46 1720.96 L1682.46 1720.96 L1682.74 1720.96 L1682.74 1720.96 L1682.46 1720.96 L1682.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1682.46,1720.96 1682.46,1720.96 1682.74,1720.96 1682.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1682.74 1720.96 L1682.74 1720.96 L1683.03 1720.96 L1683.03 1720.96 L1682.74 1720.96 L1682.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1682.74,1720.96 1682.74,1720.96 1683.03,1720.96 1682.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1683.03 1720.96 L1683.03 1720.96 L1683.31 1720.96 L1683.31 1720.96 L1683.03 1720.96 L1683.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1683.03,1720.96 1683.03,1720.96 1683.31,1720.96 1683.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1683.31 1720.96 L1683.31 1720.96 L1683.59 1720.96 L1683.59 1720.96 L1683.31 1720.96 L1683.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1683.31,1720.96 1683.31,1720.96 1683.59,1720.96 1683.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1683.59 1720.96 L1683.59 1720.96 L1683.87 1720.96 L1683.87 1720.96 L1683.59 1720.96 L1683.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1683.59,1720.96 1683.59,1720.96 1683.87,1720.96 1683.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1683.87 1720.96 L1683.87 1720.96 L1684.15 1720.96 L1684.15 1720.96 L1683.87 1720.96 L1683.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1683.87,1720.96 1683.87,1720.96 1684.15,1720.96 1683.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1684.15 1720.96 L1684.15 1720.96 L1684.44 1720.96 L1684.44 1720.96 L1684.15 1720.96 L1684.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1684.15,1720.96 1684.15,1720.96 1684.44,1720.96 1684.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1684.44 1720.96 L1684.44 1720.96 L1684.72 1720.96 L1684.72 1720.96 L1684.44 1720.96 L1684.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1684.44,1720.96 1684.44,1720.96 1684.72,1720.96 1684.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1684.72 1720.96 L1684.72 1720.96 L1685 1720.96 L1685 1720.96 L1684.72 1720.96 L1684.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1684.72,1720.96 1684.72,1720.96 1685,1720.96 1684.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1685 1720.96 L1685 1720.96 L1685.28 1720.96 L1685.28 1720.96 L1685 1720.96 L1685 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1685,1720.96 1685,1720.96 1685.28,1720.96 1685,1720.96 "/>
<path clip-path="url(#clip322)" d="M1685.28 1720.96 L1685.28 1720.96 L1685.56 1720.96 L1685.56 1720.96 L1685.28 1720.96 L1685.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1685.28,1720.96 1685.28,1720.96 1685.56,1720.96 1685.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1685.56 1720.96 L1685.56 1720.96 L1685.84 1720.96 L1685.84 1720.96 L1685.56 1720.96 L1685.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1685.56,1720.96 1685.56,1720.96 1685.84,1720.96 1685.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1685.84 1720.96 L1685.84 1720.96 L1686.13 1720.96 L1686.13 1720.96 L1685.84 1720.96 L1685.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1685.84,1720.96 1685.84,1720.96 1686.13,1720.96 1685.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1686.13 1720.96 L1686.13 1720.96 L1686.41 1720.96 L1686.41 1720.96 L1686.13 1720.96 L1686.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1686.13,1720.96 1686.13,1720.96 1686.41,1720.96 1686.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1686.41 1720.96 L1686.41 1720.96 L1686.69 1720.96 L1686.69 1720.96 L1686.41 1720.96 L1686.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1686.41,1720.96 1686.41,1720.96 1686.69,1720.96 1686.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1686.69 1720.96 L1686.69 1720.96 L1686.97 1720.96 L1686.97 1720.96 L1686.69 1720.96 L1686.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1686.69,1720.96 1686.69,1720.96 1686.97,1720.96 1686.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1686.97 1720.96 L1686.97 1720.96 L1687.25 1720.96 L1687.25 1720.96 L1686.97 1720.96 L1686.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1686.97,1720.96 1686.97,1720.96 1687.25,1720.96 1686.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1687.25 1720.96 L1687.25 1720.96 L1687.53 1720.96 L1687.53 1720.96 L1687.25 1720.96 L1687.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1687.25,1720.96 1687.25,1720.96 1687.53,1720.96 1687.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1687.53 1720.96 L1687.53 1720.96 L1687.82 1720.96 L1687.82 1720.96 L1687.53 1720.96 L1687.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1687.53,1720.96 1687.53,1720.96 1687.82,1720.96 1687.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1687.82 1720.96 L1687.82 1720.96 L1688.1 1720.96 L1688.1 1720.96 L1687.82 1720.96 L1687.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1687.82,1720.96 1687.82,1720.96 1688.1,1720.96 1687.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1688.1 1720.96 L1688.1 1720.96 L1688.38 1720.96 L1688.38 1720.96 L1688.1 1720.96 L1688.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1688.1,1720.96 1688.1,1720.96 1688.38,1720.96 1688.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1688.38 1720.96 L1688.38 1720.96 L1688.66 1720.96 L1688.66 1720.96 L1688.38 1720.96 L1688.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1688.38,1720.96 1688.38,1720.96 1688.66,1720.96 1688.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1688.66 1720.96 L1688.66 1720.96 L1688.94 1720.96 L1688.94 1720.96 L1688.66 1720.96 L1688.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1688.66,1720.96 1688.66,1720.96 1688.94,1720.96 1688.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1688.94 1720.96 L1688.94 1720.96 L1689.22 1720.96 L1689.22 1720.96 L1688.94 1720.96 L1688.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1688.94,1720.96 1688.94,1720.96 1689.22,1720.96 1688.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1689.22 1720.96 L1689.22 1720.96 L1689.51 1720.96 L1689.51 1720.96 L1689.22 1720.96 L1689.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1689.22,1720.96 1689.22,1720.96 1689.51,1720.96 1689.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1689.51 1720.96 L1689.51 1720.96 L1689.79 1720.96 L1689.79 1720.96 L1689.51 1720.96 L1689.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1689.51,1720.96 1689.51,1720.96 1689.79,1720.96 1689.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1689.79 1720.96 L1689.79 1720.96 L1690.07 1720.96 L1690.07 1720.96 L1689.79 1720.96 L1689.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1689.79,1720.96 1689.79,1720.96 1690.07,1720.96 1689.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1690.07 1720.96 L1690.07 1720.96 L1690.35 1720.96 L1690.35 1720.96 L1690.07 1720.96 L1690.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1690.07,1720.96 1690.07,1720.96 1690.35,1720.96 1690.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1690.35 1720.96 L1690.35 1720.96 L1690.63 1720.96 L1690.63 1720.96 L1690.35 1720.96 L1690.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1690.35,1720.96 1690.35,1720.96 1690.63,1720.96 1690.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1690.63 1720.96 L1690.63 1720.96 L1690.91 1720.96 L1690.91 1720.96 L1690.63 1720.96 L1690.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1690.63,1720.96 1690.63,1720.96 1690.91,1720.96 1690.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1690.91 1720.96 L1690.91 1720.96 L1691.2 1720.96 L1691.2 1720.96 L1690.91 1720.96 L1690.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1690.91,1720.96 1690.91,1720.96 1691.2,1720.96 1690.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1691.2 1720.96 L1691.2 1720.96 L1691.48 1720.96 L1691.48 1720.96 L1691.2 1720.96 L1691.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1691.2,1720.96 1691.2,1720.96 1691.48,1720.96 1691.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1691.48 1720.96 L1691.48 1720.96 L1691.76 1720.96 L1691.76 1720.96 L1691.48 1720.96 L1691.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1691.48,1720.96 1691.48,1720.96 1691.76,1720.96 1691.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1691.76 1720.96 L1691.76 1720.96 L1692.04 1720.96 L1692.04 1720.96 L1691.76 1720.96 L1691.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1691.76,1720.96 1691.76,1720.96 1692.04,1720.96 1691.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1692.04 1720.96 L1692.04 1720.96 L1692.32 1720.96 L1692.32 1720.96 L1692.04 1720.96 L1692.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1692.04,1720.96 1692.04,1720.96 1692.32,1720.96 1692.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1692.32 1720.96 L1692.32 1720.96 L1692.61 1720.96 L1692.61 1720.96 L1692.32 1720.96 L1692.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1692.32,1720.96 1692.32,1720.96 1692.61,1720.96 1692.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1692.61 1720.96 L1692.61 1720.96 L1692.89 1720.96 L1692.89 1720.96 L1692.61 1720.96 L1692.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1692.61,1720.96 1692.61,1720.96 1692.89,1720.96 1692.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1692.89 1720.96 L1692.89 1720.96 L1693.17 1720.96 L1693.17 1720.96 L1692.89 1720.96 L1692.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1692.89,1720.96 1692.89,1720.96 1693.17,1720.96 1692.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1693.17 1720.96 L1693.17 1720.96 L1693.45 1720.96 L1693.45 1720.96 L1693.17 1720.96 L1693.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1693.17,1720.96 1693.17,1720.96 1693.45,1720.96 1693.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1693.45 1720.96 L1693.45 1720.96 L1693.73 1720.96 L1693.73 1720.96 L1693.45 1720.96 L1693.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1693.45,1720.96 1693.45,1720.96 1693.73,1720.96 1693.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1693.73 1720.96 L1693.73 1720.96 L1694.01 1720.96 L1694.01 1720.96 L1693.73 1720.96 L1693.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1693.73,1720.96 1693.73,1720.96 1694.01,1720.96 1693.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1694.01 1720.96 L1694.01 1720.96 L1694.3 1720.96 L1694.3 1720.96 L1694.01 1720.96 L1694.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1694.01,1720.96 1694.01,1720.96 1694.3,1720.96 1694.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1694.3 1720.96 L1694.3 1720.96 L1694.58 1720.96 L1694.58 1720.96 L1694.3 1720.96 L1694.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1694.3,1720.96 1694.3,1720.96 1694.58,1720.96 1694.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1694.58 1720.96 L1694.58 1720.96 L1694.86 1720.96 L1694.86 1720.96 L1694.58 1720.96 L1694.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1694.58,1720.96 1694.58,1720.96 1694.86,1720.96 1694.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1694.86 1720.96 L1694.86 1720.96 L1695.14 1720.96 L1695.14 1720.96 L1694.86 1720.96 L1694.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1694.86,1720.96 1694.86,1720.96 1695.14,1720.96 1694.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1695.14 1720.96 L1695.14 1720.96 L1695.42 1720.96 L1695.42 1720.96 L1695.14 1720.96 L1695.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1695.14,1720.96 1695.14,1720.96 1695.42,1720.96 1695.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1695.42 1720.96 L1695.42 1720.96 L1695.7 1720.96 L1695.7 1720.96 L1695.42 1720.96 L1695.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1695.42,1720.96 1695.42,1720.96 1695.7,1720.96 1695.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1695.7 1720.96 L1695.7 1720.96 L1695.99 1720.96 L1695.99 1720.96 L1695.7 1720.96 L1695.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1695.7,1720.96 1695.7,1720.96 1695.99,1720.96 1695.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1695.99 1720.96 L1695.99 1720.96 L1696.27 1720.96 L1696.27 1720.96 L1695.99 1720.96 L1695.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1695.99,1720.96 1695.99,1720.96 1696.27,1720.96 1695.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1696.27 1720.96 L1696.27 1720.96 L1696.55 1720.96 L1696.55 1720.96 L1696.27 1720.96 L1696.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1696.27,1720.96 1696.27,1720.96 1696.55,1720.96 1696.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1696.55 1720.96 L1696.55 1720.96 L1696.83 1720.96 L1696.83 1720.96 L1696.55 1720.96 L1696.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1696.55,1720.96 1696.55,1720.96 1696.83,1720.96 1696.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1696.83 1720.96 L1696.83 1720.96 L1697.11 1720.96 L1697.11 1720.96 L1696.83 1720.96 L1696.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1696.83,1720.96 1696.83,1720.96 1697.11,1720.96 1696.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1697.11 1720.96 L1697.11 1720.96 L1697.39 1720.96 L1697.39 1720.96 L1697.11 1720.96 L1697.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1697.11,1720.96 1697.11,1720.96 1697.39,1720.96 1697.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1697.39 1720.96 L1697.39 1720.96 L1697.68 1720.96 L1697.68 1720.96 L1697.39 1720.96 L1697.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1697.39,1720.96 1697.39,1720.96 1697.68,1720.96 1697.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1697.68 1720.96 L1697.68 1720.96 L1697.96 1720.96 L1697.96 1720.96 L1697.68 1720.96 L1697.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1697.68,1720.96 1697.68,1720.96 1697.96,1720.96 1697.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1697.96 1720.96 L1697.96 1720.96 L1698.24 1720.96 L1698.24 1720.96 L1697.96 1720.96 L1697.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1697.96,1720.96 1697.96,1720.96 1698.24,1720.96 1697.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1698.24 1720.96 L1698.24 1720.96 L1698.52 1720.96 L1698.52 1720.96 L1698.24 1720.96 L1698.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1698.24,1720.96 1698.24,1720.96 1698.52,1720.96 1698.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1698.52 1720.96 L1698.52 1720.96 L1698.8 1720.96 L1698.8 1720.96 L1698.52 1720.96 L1698.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1698.52,1720.96 1698.52,1720.96 1698.8,1720.96 1698.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1698.8 1720.96 L1698.8 1720.96 L1699.08 1720.96 L1699.08 1720.96 L1698.8 1720.96 L1698.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1698.8,1720.96 1698.8,1720.96 1699.08,1720.96 1698.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1699.08 1720.96 L1699.08 1720.96 L1699.37 1720.96 L1699.37 1720.96 L1699.08 1720.96 L1699.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1699.08,1720.96 1699.08,1720.96 1699.37,1720.96 1699.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1699.37 1720.96 L1699.37 1720.96 L1699.65 1720.96 L1699.65 1720.96 L1699.37 1720.96 L1699.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1699.37,1720.96 1699.37,1720.96 1699.65,1720.96 1699.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1699.65 1720.96 L1699.65 1720.96 L1699.93 1720.96 L1699.93 1720.96 L1699.65 1720.96 L1699.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1699.65,1720.96 1699.65,1720.96 1699.93,1720.96 1699.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1699.93 1720.96 L1699.93 1720.96 L1700.21 1720.96 L1700.21 1720.96 L1699.93 1720.96 L1699.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1699.93,1720.96 1699.93,1720.96 1700.21,1720.96 1699.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1700.21 1720.96 L1700.21 1720.96 L1700.49 1720.96 L1700.49 1720.96 L1700.21 1720.96 L1700.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1700.21,1720.96 1700.21,1720.96 1700.49,1720.96 1700.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1700.49 1720.96 L1700.49 1720.96 L1700.78 1720.96 L1700.78 1720.96 L1700.49 1720.96 L1700.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1700.49,1720.96 1700.49,1720.96 1700.78,1720.96 1700.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1700.78 1720.96 L1700.78 1720.96 L1701.06 1720.96 L1701.06 1720.96 L1700.78 1720.96 L1700.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1700.78,1720.96 1700.78,1720.96 1701.06,1720.96 1700.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1701.06 1720.96 L1701.06 1720.96 L1701.34 1720.96 L1701.34 1720.96 L1701.06 1720.96 L1701.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1701.06,1720.96 1701.06,1720.96 1701.34,1720.96 1701.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1701.34 1720.96 L1701.34 1720.96 L1701.62 1720.96 L1701.62 1720.96 L1701.34 1720.96 L1701.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1701.34,1720.96 1701.34,1720.96 1701.62,1720.96 1701.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1701.62 1720.96 L1701.62 1720.96 L1701.9 1720.96 L1701.9 1720.96 L1701.62 1720.96 L1701.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1701.62,1720.96 1701.62,1720.96 1701.9,1720.96 1701.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1701.9 1720.96 L1701.9 1720.96 L1702.18 1720.96 L1702.18 1720.96 L1701.9 1720.96 L1701.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1701.9,1720.96 1701.9,1720.96 1702.18,1720.96 1701.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1702.18 1720.96 L1702.18 1720.96 L1702.47 1720.96 L1702.47 1720.96 L1702.18 1720.96 L1702.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1702.18,1720.96 1702.18,1720.96 1702.47,1720.96 1702.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1702.47 1720.96 L1702.47 1720.96 L1702.75 1720.96 L1702.75 1720.96 L1702.47 1720.96 L1702.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1702.47,1720.96 1702.47,1720.96 1702.75,1720.96 1702.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1702.75 1720.96 L1702.75 1720.96 L1703.03 1720.96 L1703.03 1720.96 L1702.75 1720.96 L1702.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1702.75,1720.96 1702.75,1720.96 1703.03,1720.96 1702.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1703.03 1720.96 L1703.03 1720.96 L1703.31 1720.96 L1703.31 1720.96 L1703.03 1720.96 L1703.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1703.03,1720.96 1703.03,1720.96 1703.31,1720.96 1703.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1703.31 1720.96 L1703.31 1720.96 L1703.59 1720.96 L1703.59 1720.96 L1703.31 1720.96 L1703.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1703.31,1720.96 1703.31,1720.96 1703.59,1720.96 1703.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1703.59 1720.96 L1703.59 1720.96 L1703.87 1720.96 L1703.87 1720.96 L1703.59 1720.96 L1703.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1703.59,1720.96 1703.59,1720.96 1703.87,1720.96 1703.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1703.87 1720.96 L1703.87 1720.96 L1704.16 1720.96 L1704.16 1720.96 L1703.87 1720.96 L1703.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1703.87,1720.96 1703.87,1720.96 1704.16,1720.96 1703.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1704.16 1720.96 L1704.16 1720.96 L1704.44 1720.96 L1704.44 1720.96 L1704.16 1720.96 L1704.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1704.16,1720.96 1704.16,1720.96 1704.44,1720.96 1704.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1704.44 1720.96 L1704.44 1720.96 L1704.72 1720.96 L1704.72 1720.96 L1704.44 1720.96 L1704.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1704.44,1720.96 1704.44,1720.96 1704.72,1720.96 1704.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1704.72 1720.96 L1704.72 1720.96 L1705 1720.96 L1705 1720.96 L1704.72 1720.96 L1704.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1704.72,1720.96 1704.72,1720.96 1705,1720.96 1704.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1705 1720.96 L1705 1720.96 L1705.28 1720.96 L1705.28 1720.96 L1705 1720.96 L1705 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1705,1720.96 1705,1720.96 1705.28,1720.96 1705,1720.96 "/>
<path clip-path="url(#clip322)" d="M1705.28 1720.96 L1705.28 1720.96 L1705.56 1720.96 L1705.56 1720.96 L1705.28 1720.96 L1705.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1705.28,1720.96 1705.28,1720.96 1705.56,1720.96 1705.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1705.56 1720.96 L1705.56 1720.96 L1705.85 1720.96 L1705.85 1720.96 L1705.56 1720.96 L1705.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1705.56,1720.96 1705.56,1720.96 1705.85,1720.96 1705.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1705.85 1720.96 L1705.85 1720.96 L1706.13 1720.96 L1706.13 1720.96 L1705.85 1720.96 L1705.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1705.85,1720.96 1705.85,1720.96 1706.13,1720.96 1705.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1706.13 1720.96 L1706.13 1720.96 L1706.41 1720.96 L1706.41 1720.96 L1706.13 1720.96 L1706.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1706.13,1720.96 1706.13,1720.96 1706.41,1720.96 1706.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1706.41 1720.96 L1706.41 1720.96 L1706.69 1720.96 L1706.69 1720.96 L1706.41 1720.96 L1706.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1706.41,1720.96 1706.41,1720.96 1706.69,1720.96 1706.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1706.69 1720.96 L1706.69 1720.96 L1706.97 1720.96 L1706.97 1720.96 L1706.69 1720.96 L1706.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1706.69,1720.96 1706.69,1720.96 1706.97,1720.96 1706.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1706.97 1720.96 L1706.97 1720.96 L1707.25 1720.96 L1707.25 1720.96 L1706.97 1720.96 L1706.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1706.97,1720.96 1706.97,1720.96 1707.25,1720.96 1706.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1707.25 1720.96 L1707.25 1720.96 L1707.54 1720.96 L1707.54 1720.96 L1707.25 1720.96 L1707.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1707.25,1720.96 1707.25,1720.96 1707.54,1720.96 1707.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1707.54 1720.96 L1707.54 1720.96 L1707.82 1720.96 L1707.82 1720.96 L1707.54 1720.96 L1707.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1707.54,1720.96 1707.54,1720.96 1707.82,1720.96 1707.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1707.82 1720.96 L1707.82 1720.96 L1708.1 1720.96 L1708.1 1720.96 L1707.82 1720.96 L1707.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1707.82,1720.96 1707.82,1720.96 1708.1,1720.96 1707.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1708.1 1720.96 L1708.1 1720.96 L1708.38 1720.96 L1708.38 1720.96 L1708.1 1720.96 L1708.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1708.1,1720.96 1708.1,1720.96 1708.38,1720.96 1708.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1708.38 1720.96 L1708.38 1720.96 L1708.66 1720.96 L1708.66 1720.96 L1708.38 1720.96 L1708.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1708.38,1720.96 1708.38,1720.96 1708.66,1720.96 1708.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1708.66 1720.96 L1708.66 1720.96 L1708.95 1720.96 L1708.95 1720.96 L1708.66 1720.96 L1708.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1708.66,1720.96 1708.66,1720.96 1708.95,1720.96 1708.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1708.95 1720.96 L1708.95 1720.96 L1709.23 1720.96 L1709.23 1720.96 L1708.95 1720.96 L1708.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1708.95,1720.96 1708.95,1720.96 1709.23,1720.96 1708.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1709.23 1720.96 L1709.23 1720.96 L1709.51 1720.96 L1709.51 1720.96 L1709.23 1720.96 L1709.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1709.23,1720.96 1709.23,1720.96 1709.51,1720.96 1709.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1709.51 1720.96 L1709.51 1720.96 L1709.79 1720.96 L1709.79 1720.96 L1709.51 1720.96 L1709.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1709.51,1720.96 1709.51,1720.96 1709.79,1720.96 1709.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1709.79 1720.96 L1709.79 1720.96 L1710.07 1720.96 L1710.07 1720.96 L1709.79 1720.96 L1709.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1709.79,1720.96 1709.79,1720.96 1710.07,1720.96 1709.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1710.07 1720.96 L1710.07 1720.96 L1710.35 1720.96 L1710.35 1720.96 L1710.07 1720.96 L1710.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1710.07,1720.96 1710.07,1720.96 1710.35,1720.96 1710.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1710.35 1720.96 L1710.35 1720.96 L1710.64 1720.96 L1710.64 1720.96 L1710.35 1720.96 L1710.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1710.35,1720.96 1710.35,1720.96 1710.64,1720.96 1710.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1710.64 1720.96 L1710.64 1720.96 L1710.92 1720.96 L1710.92 1720.96 L1710.64 1720.96 L1710.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1710.64,1720.96 1710.64,1720.96 1710.92,1720.96 1710.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1710.92 1720.96 L1710.92 1720.96 L1711.2 1720.96 L1711.2 1720.96 L1710.92 1720.96 L1710.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1710.92,1720.96 1710.92,1720.96 1711.2,1720.96 1710.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1711.2 1720.76 L1711.2 1720.96 L1711.48 1720.96 L1711.48 1720.76 L1711.2 1720.76 L1711.2 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1711.2,1720.76 1711.2,1720.96 1711.48,1720.96 1711.48,1720.76 1711.2,1720.76 "/>
<path clip-path="url(#clip322)" d="M1711.48 1720.96 L1711.48 1720.96 L1711.76 1720.96 L1711.76 1720.96 L1711.48 1720.96 L1711.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1711.48,1720.96 1711.48,1720.96 1711.76,1720.96 1711.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1711.76 1720.96 L1711.76 1720.96 L1712.04 1720.96 L1712.04 1720.96 L1711.76 1720.96 L1711.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1711.76,1720.96 1711.76,1720.96 1712.04,1720.96 1711.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1712.04 1720.96 L1712.04 1720.96 L1712.33 1720.96 L1712.33 1720.96 L1712.04 1720.96 L1712.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1712.04,1720.96 1712.04,1720.96 1712.33,1720.96 1712.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1712.33 1720.96 L1712.33 1720.96 L1712.61 1720.96 L1712.61 1720.96 L1712.33 1720.96 L1712.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1712.33,1720.96 1712.33,1720.96 1712.61,1720.96 1712.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1712.61 1720.96 L1712.61 1720.96 L1712.89 1720.96 L1712.89 1720.96 L1712.61 1720.96 L1712.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1712.61,1720.96 1712.61,1720.96 1712.89,1720.96 1712.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1712.89 1720.96 L1712.89 1720.96 L1713.17 1720.96 L1713.17 1720.96 L1712.89 1720.96 L1712.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1712.89,1720.96 1712.89,1720.96 1713.17,1720.96 1712.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1713.17 1720.96 L1713.17 1720.96 L1713.45 1720.96 L1713.45 1720.96 L1713.17 1720.96 L1713.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1713.17,1720.96 1713.17,1720.96 1713.45,1720.96 1713.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1713.45 1720.96 L1713.45 1720.96 L1713.73 1720.96 L1713.73 1720.96 L1713.45 1720.96 L1713.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1713.45,1720.96 1713.45,1720.96 1713.73,1720.96 1713.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1713.73 1720.96 L1713.73 1720.96 L1714.02 1720.96 L1714.02 1720.96 L1713.73 1720.96 L1713.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1713.73,1720.96 1713.73,1720.96 1714.02,1720.96 1713.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1714.02 1720.96 L1714.02 1720.96 L1714.3 1720.96 L1714.3 1720.96 L1714.02 1720.96 L1714.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1714.02,1720.96 1714.02,1720.96 1714.3,1720.96 1714.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1714.3 1720.96 L1714.3 1720.96 L1714.58 1720.96 L1714.58 1720.96 L1714.3 1720.96 L1714.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1714.3,1720.96 1714.3,1720.96 1714.58,1720.96 1714.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1714.58 1720.96 L1714.58 1720.96 L1714.86 1720.96 L1714.86 1720.96 L1714.58 1720.96 L1714.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1714.58,1720.96 1714.58,1720.96 1714.86,1720.96 1714.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1714.86 1720.96 L1714.86 1720.96 L1715.14 1720.96 L1715.14 1720.96 L1714.86 1720.96 L1714.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1714.86,1720.96 1714.86,1720.96 1715.14,1720.96 1714.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1715.14 1720.96 L1715.14 1720.96 L1715.43 1720.96 L1715.43 1720.96 L1715.14 1720.96 L1715.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1715.14,1720.96 1715.14,1720.96 1715.43,1720.96 1715.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1715.43 1720.96 L1715.43 1720.96 L1715.71 1720.96 L1715.71 1720.96 L1715.43 1720.96 L1715.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1715.43,1720.96 1715.43,1720.96 1715.71,1720.96 1715.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1715.71 1720.96 L1715.71 1720.96 L1715.99 1720.96 L1715.99 1720.96 L1715.71 1720.96 L1715.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1715.71,1720.96 1715.71,1720.96 1715.99,1720.96 1715.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1715.99 1720.96 L1715.99 1720.96 L1716.27 1720.96 L1716.27 1720.96 L1715.99 1720.96 L1715.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1715.99,1720.96 1715.99,1720.96 1716.27,1720.96 1715.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1716.27 1720.96 L1716.27 1720.96 L1716.55 1720.96 L1716.55 1720.96 L1716.27 1720.96 L1716.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1716.27,1720.96 1716.27,1720.96 1716.55,1720.96 1716.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1716.55 1720.96 L1716.55 1720.96 L1716.83 1720.96 L1716.83 1720.96 L1716.55 1720.96 L1716.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1716.55,1720.96 1716.55,1720.96 1716.83,1720.96 1716.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1716.83 1720.96 L1716.83 1720.96 L1717.12 1720.96 L1717.12 1720.96 L1716.83 1720.96 L1716.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1716.83,1720.96 1716.83,1720.96 1717.12,1720.96 1716.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1717.12 1720.96 L1717.12 1720.96 L1717.4 1720.96 L1717.4 1720.96 L1717.12 1720.96 L1717.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1717.12,1720.96 1717.12,1720.96 1717.4,1720.96 1717.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1717.4 1720.96 L1717.4 1720.96 L1717.68 1720.96 L1717.68 1720.96 L1717.4 1720.96 L1717.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1717.4,1720.96 1717.4,1720.96 1717.68,1720.96 1717.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1717.68 1720.96 L1717.68 1720.96 L1717.96 1720.96 L1717.96 1720.96 L1717.68 1720.96 L1717.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1717.68,1720.96 1717.68,1720.96 1717.96,1720.96 1717.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1717.96 1720.96 L1717.96 1720.96 L1718.24 1720.96 L1718.24 1720.96 L1717.96 1720.96 L1717.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1717.96,1720.96 1717.96,1720.96 1718.24,1720.96 1717.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1718.24 1720.96 L1718.24 1720.96 L1718.52 1720.96 L1718.52 1720.96 L1718.24 1720.96 L1718.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1718.24,1720.96 1718.24,1720.96 1718.52,1720.96 1718.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1718.52 1720.96 L1718.52 1720.96 L1718.81 1720.96 L1718.81 1720.96 L1718.52 1720.96 L1718.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1718.52,1720.96 1718.52,1720.96 1718.81,1720.96 1718.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1718.81 1720.96 L1718.81 1720.96 L1719.09 1720.96 L1719.09 1720.96 L1718.81 1720.96 L1718.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1718.81,1720.96 1718.81,1720.96 1719.09,1720.96 1718.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1719.09 1720.96 L1719.09 1720.96 L1719.37 1720.96 L1719.37 1720.96 L1719.09 1720.96 L1719.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1719.09,1720.96 1719.09,1720.96 1719.37,1720.96 1719.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1719.37 1720.96 L1719.37 1720.96 L1719.65 1720.96 L1719.65 1720.96 L1719.37 1720.96 L1719.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1719.37,1720.96 1719.37,1720.96 1719.65,1720.96 1719.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1719.65 1720.96 L1719.65 1720.96 L1719.93 1720.96 L1719.93 1720.96 L1719.65 1720.96 L1719.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1719.65,1720.96 1719.65,1720.96 1719.93,1720.96 1719.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1719.93 1720.96 L1719.93 1720.96 L1720.21 1720.96 L1720.21 1720.96 L1719.93 1720.96 L1719.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1719.93,1720.96 1719.93,1720.96 1720.21,1720.96 1719.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1720.21 1720.96 L1720.21 1720.96 L1720.5 1720.96 L1720.5 1720.96 L1720.21 1720.96 L1720.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1720.21,1720.96 1720.21,1720.96 1720.5,1720.96 1720.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1720.5 1720.96 L1720.5 1720.96 L1720.78 1720.96 L1720.78 1720.96 L1720.5 1720.96 L1720.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1720.5,1720.96 1720.5,1720.96 1720.78,1720.96 1720.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1720.78 1720.96 L1720.78 1720.96 L1721.06 1720.96 L1721.06 1720.96 L1720.78 1720.96 L1720.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1720.78,1720.96 1720.78,1720.96 1721.06,1720.96 1720.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1721.06 1720.96 L1721.06 1720.96 L1721.34 1720.96 L1721.34 1720.96 L1721.06 1720.96 L1721.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1721.06,1720.96 1721.06,1720.96 1721.34,1720.96 1721.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1721.34 1720.96 L1721.34 1720.96 L1721.62 1720.96 L1721.62 1720.96 L1721.34 1720.96 L1721.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1721.34,1720.96 1721.34,1720.96 1721.62,1720.96 1721.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1721.62 1720.96 L1721.62 1720.96 L1721.9 1720.96 L1721.9 1720.96 L1721.62 1720.96 L1721.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1721.62,1720.96 1721.62,1720.96 1721.9,1720.96 1721.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1721.9 1720.96 L1721.9 1720.96 L1722.19 1720.96 L1722.19 1720.96 L1721.9 1720.96 L1721.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1721.9,1720.96 1721.9,1720.96 1722.19,1720.96 1721.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1722.19 1720.96 L1722.19 1720.96 L1722.47 1720.96 L1722.47 1720.96 L1722.19 1720.96 L1722.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1722.19,1720.96 1722.19,1720.96 1722.47,1720.96 1722.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1722.47 1720.96 L1722.47 1720.96 L1722.75 1720.96 L1722.75 1720.96 L1722.47 1720.96 L1722.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1722.47,1720.96 1722.47,1720.96 1722.75,1720.96 1722.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1722.75 1720.96 L1722.75 1720.96 L1723.03 1720.96 L1723.03 1720.96 L1722.75 1720.96 L1722.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1722.75,1720.96 1722.75,1720.96 1723.03,1720.96 1722.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1723.03 1720.96 L1723.03 1720.96 L1723.31 1720.96 L1723.31 1720.96 L1723.03 1720.96 L1723.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1723.03,1720.96 1723.03,1720.96 1723.31,1720.96 1723.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1723.31 1720.96 L1723.31 1720.96 L1723.6 1720.96 L1723.6 1720.96 L1723.31 1720.96 L1723.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1723.31,1720.96 1723.31,1720.96 1723.6,1720.96 1723.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1723.6 1720.96 L1723.6 1720.96 L1723.88 1720.96 L1723.88 1720.96 L1723.6 1720.96 L1723.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1723.6,1720.96 1723.6,1720.96 1723.88,1720.96 1723.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1723.88 1720.96 L1723.88 1720.96 L1724.16 1720.96 L1724.16 1720.96 L1723.88 1720.96 L1723.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1723.88,1720.96 1723.88,1720.96 1724.16,1720.96 1723.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1724.16 1720.96 L1724.16 1720.96 L1724.44 1720.96 L1724.44 1720.96 L1724.16 1720.96 L1724.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1724.16,1720.96 1724.16,1720.96 1724.44,1720.96 1724.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1724.44 1720.96 L1724.44 1720.96 L1724.72 1720.96 L1724.72 1720.96 L1724.44 1720.96 L1724.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1724.44,1720.96 1724.44,1720.96 1724.72,1720.96 1724.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1724.72 1720.96 L1724.72 1720.96 L1725 1720.96 L1725 1720.96 L1724.72 1720.96 L1724.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1724.72,1720.96 1724.72,1720.96 1725,1720.96 1724.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1725 1720.96 L1725 1720.96 L1725.29 1720.96 L1725.29 1720.96 L1725 1720.96 L1725 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1725,1720.96 1725,1720.96 1725.29,1720.96 1725,1720.96 "/>
<path clip-path="url(#clip322)" d="M1725.29 1720.96 L1725.29 1720.96 L1725.57 1720.96 L1725.57 1720.96 L1725.29 1720.96 L1725.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1725.29,1720.96 1725.29,1720.96 1725.57,1720.96 1725.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1725.57 1720.96 L1725.57 1720.96 L1725.85 1720.96 L1725.85 1720.96 L1725.57 1720.96 L1725.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1725.57,1720.96 1725.57,1720.96 1725.85,1720.96 1725.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1725.85 1720.96 L1725.85 1720.96 L1726.13 1720.96 L1726.13 1720.96 L1725.85 1720.96 L1725.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1725.85,1720.96 1725.85,1720.96 1726.13,1720.96 1725.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1726.13 1720.96 L1726.13 1720.96 L1726.41 1720.96 L1726.41 1720.96 L1726.13 1720.96 L1726.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1726.13,1720.96 1726.13,1720.96 1726.41,1720.96 1726.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1726.41 1720.96 L1726.41 1720.96 L1726.69 1720.96 L1726.69 1720.96 L1726.41 1720.96 L1726.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1726.41,1720.96 1726.41,1720.96 1726.69,1720.96 1726.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1726.69 1720.96 L1726.69 1720.96 L1726.98 1720.96 L1726.98 1720.96 L1726.69 1720.96 L1726.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1726.69,1720.96 1726.69,1720.96 1726.98,1720.96 1726.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1726.98 1720.96 L1726.98 1720.96 L1727.26 1720.96 L1727.26 1720.96 L1726.98 1720.96 L1726.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1726.98,1720.96 1726.98,1720.96 1727.26,1720.96 1726.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1727.26 1720.96 L1727.26 1720.96 L1727.54 1720.96 L1727.54 1720.96 L1727.26 1720.96 L1727.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1727.26,1720.96 1727.26,1720.96 1727.54,1720.96 1727.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1727.54 1720.96 L1727.54 1720.96 L1727.82 1720.96 L1727.82 1720.96 L1727.54 1720.96 L1727.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1727.54,1720.96 1727.54,1720.96 1727.82,1720.96 1727.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1727.82 1720.96 L1727.82 1720.96 L1728.1 1720.96 L1728.1 1720.96 L1727.82 1720.96 L1727.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1727.82,1720.96 1727.82,1720.96 1728.1,1720.96 1727.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1728.1 1720.96 L1728.1 1720.96 L1728.38 1720.96 L1728.38 1720.96 L1728.1 1720.96 L1728.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1728.1,1720.96 1728.1,1720.96 1728.38,1720.96 1728.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1728.38 1720.96 L1728.38 1720.96 L1728.67 1720.96 L1728.67 1720.96 L1728.38 1720.96 L1728.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1728.38,1720.96 1728.38,1720.96 1728.67,1720.96 1728.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1728.67 1720.96 L1728.67 1720.96 L1728.95 1720.96 L1728.95 1720.96 L1728.67 1720.96 L1728.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1728.67,1720.96 1728.67,1720.96 1728.95,1720.96 1728.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1728.95 1720.96 L1728.95 1720.96 L1729.23 1720.96 L1729.23 1720.96 L1728.95 1720.96 L1728.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1728.95,1720.96 1728.95,1720.96 1729.23,1720.96 1728.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1729.23 1720.96 L1729.23 1720.96 L1729.51 1720.96 L1729.51 1720.96 L1729.23 1720.96 L1729.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1729.23,1720.96 1729.23,1720.96 1729.51,1720.96 1729.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1729.51 1720.96 L1729.51 1720.96 L1729.79 1720.96 L1729.79 1720.96 L1729.51 1720.96 L1729.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1729.51,1720.96 1729.51,1720.96 1729.79,1720.96 1729.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1729.79 1720.96 L1729.79 1720.96 L1730.07 1720.96 L1730.07 1720.96 L1729.79 1720.96 L1729.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1729.79,1720.96 1729.79,1720.96 1730.07,1720.96 1729.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1730.07 1720.96 L1730.07 1720.96 L1730.36 1720.96 L1730.36 1720.96 L1730.07 1720.96 L1730.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1730.07,1720.96 1730.07,1720.96 1730.36,1720.96 1730.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1730.36 1720.96 L1730.36 1720.96 L1730.64 1720.96 L1730.64 1720.96 L1730.36 1720.96 L1730.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1730.36,1720.96 1730.36,1720.96 1730.64,1720.96 1730.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1730.64 1720.96 L1730.64 1720.96 L1730.92 1720.96 L1730.92 1720.96 L1730.64 1720.96 L1730.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1730.64,1720.96 1730.64,1720.96 1730.92,1720.96 1730.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1730.92 1720.96 L1730.92 1720.96 L1731.2 1720.96 L1731.2 1720.96 L1730.92 1720.96 L1730.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1730.92,1720.96 1730.92,1720.96 1731.2,1720.96 1730.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1731.2 1720.96 L1731.2 1720.96 L1731.48 1720.96 L1731.48 1720.96 L1731.2 1720.96 L1731.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1731.2,1720.96 1731.2,1720.96 1731.48,1720.96 1731.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1731.48 1720.96 L1731.48 1720.96 L1731.77 1720.96 L1731.77 1720.96 L1731.48 1720.96 L1731.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1731.48,1720.96 1731.48,1720.96 1731.77,1720.96 1731.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1731.77 1720.96 L1731.77 1720.96 L1732.05 1720.96 L1732.05 1720.96 L1731.77 1720.96 L1731.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1731.77,1720.96 1731.77,1720.96 1732.05,1720.96 1731.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1732.05 1720.96 L1732.05 1720.96 L1732.33 1720.96 L1732.33 1720.96 L1732.05 1720.96 L1732.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1732.05,1720.96 1732.05,1720.96 1732.33,1720.96 1732.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1732.33 1720.96 L1732.33 1720.96 L1732.61 1720.96 L1732.61 1720.96 L1732.33 1720.96 L1732.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1732.33,1720.96 1732.33,1720.96 1732.61,1720.96 1732.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1732.61 1720.96 L1732.61 1720.96 L1732.89 1720.96 L1732.89 1720.96 L1732.61 1720.96 L1732.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1732.61,1720.96 1732.61,1720.96 1732.89,1720.96 1732.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1732.89 1720.96 L1732.89 1720.96 L1733.17 1720.96 L1733.17 1720.96 L1732.89 1720.96 L1732.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1732.89,1720.96 1732.89,1720.96 1733.17,1720.96 1732.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1733.17 1720.96 L1733.17 1720.96 L1733.46 1720.96 L1733.46 1720.96 L1733.17 1720.96 L1733.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1733.17,1720.96 1733.17,1720.96 1733.46,1720.96 1733.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1733.46 1720.96 L1733.46 1720.96 L1733.74 1720.96 L1733.74 1720.96 L1733.46 1720.96 L1733.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1733.46,1720.96 1733.46,1720.96 1733.74,1720.96 1733.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1733.74 1720.96 L1733.74 1720.96 L1734.02 1720.96 L1734.02 1720.96 L1733.74 1720.96 L1733.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1733.74,1720.96 1733.74,1720.96 1734.02,1720.96 1733.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1734.02 1720.96 L1734.02 1720.96 L1734.3 1720.96 L1734.3 1720.96 L1734.02 1720.96 L1734.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1734.02,1720.96 1734.02,1720.96 1734.3,1720.96 1734.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1734.3 1720.96 L1734.3 1720.96 L1734.58 1720.96 L1734.58 1720.96 L1734.3 1720.96 L1734.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1734.3,1720.96 1734.3,1720.96 1734.58,1720.96 1734.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1734.58 1720.96 L1734.58 1720.96 L1734.86 1720.96 L1734.86 1720.96 L1734.58 1720.96 L1734.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1734.58,1720.96 1734.58,1720.96 1734.86,1720.96 1734.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1734.86 1720.96 L1734.86 1720.96 L1735.15 1720.96 L1735.15 1720.96 L1734.86 1720.96 L1734.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1734.86,1720.96 1734.86,1720.96 1735.15,1720.96 1734.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1735.15 1720.76 L1735.15 1720.96 L1735.43 1720.96 L1735.43 1720.76 L1735.15 1720.76 L1735.15 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1735.15,1720.76 1735.15,1720.96 1735.43,1720.96 1735.43,1720.76 1735.15,1720.76 "/>
<path clip-path="url(#clip322)" d="M1735.43 1720.96 L1735.43 1720.96 L1735.71 1720.96 L1735.71 1720.96 L1735.43 1720.96 L1735.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1735.43,1720.96 1735.43,1720.96 1735.71,1720.96 1735.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1735.71 1720.96 L1735.71 1720.96 L1735.99 1720.96 L1735.99 1720.96 L1735.71 1720.96 L1735.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1735.71,1720.96 1735.71,1720.96 1735.99,1720.96 1735.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1735.99 1720.96 L1735.99 1720.96 L1736.27 1720.96 L1736.27 1720.96 L1735.99 1720.96 L1735.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1735.99,1720.96 1735.99,1720.96 1736.27,1720.96 1735.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1736.27 1720.96 L1736.27 1720.96 L1736.55 1720.96 L1736.55 1720.96 L1736.27 1720.96 L1736.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1736.27,1720.96 1736.27,1720.96 1736.55,1720.96 1736.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1736.55 1720.96 L1736.55 1720.96 L1736.84 1720.96 L1736.84 1720.96 L1736.55 1720.96 L1736.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1736.55,1720.96 1736.55,1720.96 1736.84,1720.96 1736.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1736.84 1720.96 L1736.84 1720.96 L1737.12 1720.96 L1737.12 1720.96 L1736.84 1720.96 L1736.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1736.84,1720.96 1736.84,1720.96 1737.12,1720.96 1736.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1737.12 1720.96 L1737.12 1720.96 L1737.4 1720.96 L1737.4 1720.96 L1737.12 1720.96 L1737.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1737.12,1720.96 1737.12,1720.96 1737.4,1720.96 1737.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1737.4 1720.96 L1737.4 1720.96 L1737.68 1720.96 L1737.68 1720.96 L1737.4 1720.96 L1737.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1737.4,1720.96 1737.4,1720.96 1737.68,1720.96 1737.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1737.68 1720.96 L1737.68 1720.96 L1737.96 1720.96 L1737.96 1720.96 L1737.68 1720.96 L1737.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1737.68,1720.96 1737.68,1720.96 1737.96,1720.96 1737.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1737.96 1720.96 L1737.96 1720.96 L1738.24 1720.96 L1738.24 1720.96 L1737.96 1720.96 L1737.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1737.96,1720.96 1737.96,1720.96 1738.24,1720.96 1737.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1738.24 1720.96 L1738.24 1720.96 L1738.53 1720.96 L1738.53 1720.96 L1738.24 1720.96 L1738.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1738.24,1720.96 1738.24,1720.96 1738.53,1720.96 1738.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1738.53 1720.96 L1738.53 1720.96 L1738.81 1720.96 L1738.81 1720.96 L1738.53 1720.96 L1738.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1738.53,1720.96 1738.53,1720.96 1738.81,1720.96 1738.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1738.81 1720.96 L1738.81 1720.96 L1739.09 1720.96 L1739.09 1720.96 L1738.81 1720.96 L1738.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1738.81,1720.96 1738.81,1720.96 1739.09,1720.96 1738.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1739.09 1720.96 L1739.09 1720.96 L1739.37 1720.96 L1739.37 1720.96 L1739.09 1720.96 L1739.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1739.09,1720.96 1739.09,1720.96 1739.37,1720.96 1739.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1739.37 1720.96 L1739.37 1720.96 L1739.65 1720.96 L1739.65 1720.96 L1739.37 1720.96 L1739.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1739.37,1720.96 1739.37,1720.96 1739.65,1720.96 1739.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1739.65 1720.96 L1739.65 1720.96 L1739.94 1720.96 L1739.94 1720.96 L1739.65 1720.96 L1739.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1739.65,1720.96 1739.65,1720.96 1739.94,1720.96 1739.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1739.94 1720.96 L1739.94 1720.96 L1740.22 1720.96 L1740.22 1720.96 L1739.94 1720.96 L1739.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1739.94,1720.96 1739.94,1720.96 1740.22,1720.96 1739.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1740.22 1720.96 L1740.22 1720.96 L1740.5 1720.96 L1740.5 1720.96 L1740.22 1720.96 L1740.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1740.22,1720.96 1740.22,1720.96 1740.5,1720.96 1740.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1740.5 1720.96 L1740.5 1720.96 L1740.78 1720.96 L1740.78 1720.96 L1740.5 1720.96 L1740.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1740.5,1720.96 1740.5,1720.96 1740.78,1720.96 1740.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1740.78 1720.96 L1740.78 1720.96 L1741.06 1720.96 L1741.06 1720.96 L1740.78 1720.96 L1740.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1740.78,1720.96 1740.78,1720.96 1741.06,1720.96 1740.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1741.06 1720.96 L1741.06 1720.96 L1741.34 1720.96 L1741.34 1720.96 L1741.06 1720.96 L1741.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1741.06,1720.96 1741.06,1720.96 1741.34,1720.96 1741.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1741.34 1720.96 L1741.34 1720.96 L1741.63 1720.96 L1741.63 1720.96 L1741.34 1720.96 L1741.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1741.34,1720.96 1741.34,1720.96 1741.63,1720.96 1741.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1741.63 1720.96 L1741.63 1720.96 L1741.91 1720.96 L1741.91 1720.96 L1741.63 1720.96 L1741.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1741.63,1720.96 1741.63,1720.96 1741.91,1720.96 1741.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1741.91 1720.96 L1741.91 1720.96 L1742.19 1720.96 L1742.19 1720.96 L1741.91 1720.96 L1741.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1741.91,1720.96 1741.91,1720.96 1742.19,1720.96 1741.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1742.19 1720.96 L1742.19 1720.96 L1742.47 1720.96 L1742.47 1720.96 L1742.19 1720.96 L1742.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1742.19,1720.96 1742.19,1720.96 1742.47,1720.96 1742.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1742.47 1720.96 L1742.47 1720.96 L1742.75 1720.96 L1742.75 1720.96 L1742.47 1720.96 L1742.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1742.47,1720.96 1742.47,1720.96 1742.75,1720.96 1742.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1742.75 1720.96 L1742.75 1720.96 L1743.03 1720.96 L1743.03 1720.96 L1742.75 1720.96 L1742.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1742.75,1720.96 1742.75,1720.96 1743.03,1720.96 1742.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1743.03 1720.96 L1743.03 1720.96 L1743.32 1720.96 L1743.32 1720.96 L1743.03 1720.96 L1743.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1743.03,1720.96 1743.03,1720.96 1743.32,1720.96 1743.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1743.32 1720.96 L1743.32 1720.96 L1743.6 1720.96 L1743.6 1720.96 L1743.32 1720.96 L1743.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1743.32,1720.96 1743.32,1720.96 1743.6,1720.96 1743.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1743.6 1720.96 L1743.6 1720.96 L1743.88 1720.96 L1743.88 1720.96 L1743.6 1720.96 L1743.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1743.6,1720.96 1743.6,1720.96 1743.88,1720.96 1743.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1743.88 1720.96 L1743.88 1720.96 L1744.16 1720.96 L1744.16 1720.96 L1743.88 1720.96 L1743.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1743.88,1720.96 1743.88,1720.96 1744.16,1720.96 1743.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1744.16 1720.96 L1744.16 1720.96 L1744.44 1720.96 L1744.44 1720.96 L1744.16 1720.96 L1744.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1744.16,1720.96 1744.16,1720.96 1744.44,1720.96 1744.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1744.44 1720.96 L1744.44 1720.96 L1744.72 1720.96 L1744.72 1720.96 L1744.44 1720.96 L1744.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1744.44,1720.96 1744.44,1720.96 1744.72,1720.96 1744.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1744.72 1720.96 L1744.72 1720.96 L1745.01 1720.96 L1745.01 1720.96 L1744.72 1720.96 L1744.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1744.72,1720.96 1744.72,1720.96 1745.01,1720.96 1744.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1745.01 1720.96 L1745.01 1720.96 L1745.29 1720.96 L1745.29 1720.96 L1745.01 1720.96 L1745.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1745.01,1720.96 1745.01,1720.96 1745.29,1720.96 1745.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1745.29 1720.96 L1745.29 1720.96 L1745.57 1720.96 L1745.57 1720.96 L1745.29 1720.96 L1745.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1745.29,1720.96 1745.29,1720.96 1745.57,1720.96 1745.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1745.57 1720.96 L1745.57 1720.96 L1745.85 1720.96 L1745.85 1720.96 L1745.57 1720.96 L1745.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1745.57,1720.96 1745.57,1720.96 1745.85,1720.96 1745.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1745.85 1720.96 L1745.85 1720.96 L1746.13 1720.96 L1746.13 1720.96 L1745.85 1720.96 L1745.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1745.85,1720.96 1745.85,1720.96 1746.13,1720.96 1745.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1746.13 1720.96 L1746.13 1720.96 L1746.41 1720.96 L1746.41 1720.96 L1746.13 1720.96 L1746.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1746.13,1720.96 1746.13,1720.96 1746.41,1720.96 1746.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1746.41 1720.96 L1746.41 1720.96 L1746.7 1720.96 L1746.7 1720.96 L1746.41 1720.96 L1746.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1746.41,1720.96 1746.41,1720.96 1746.7,1720.96 1746.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1746.7 1720.96 L1746.7 1720.96 L1746.98 1720.96 L1746.98 1720.96 L1746.7 1720.96 L1746.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1746.7,1720.96 1746.7,1720.96 1746.98,1720.96 1746.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1746.98 1720.96 L1746.98 1720.96 L1747.26 1720.96 L1747.26 1720.96 L1746.98 1720.96 L1746.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1746.98,1720.96 1746.98,1720.96 1747.26,1720.96 1746.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1747.26 1720.96 L1747.26 1720.96 L1747.54 1720.96 L1747.54 1720.96 L1747.26 1720.96 L1747.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1747.26,1720.96 1747.26,1720.96 1747.54,1720.96 1747.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1747.54 1720.96 L1747.54 1720.96 L1747.82 1720.96 L1747.82 1720.96 L1747.54 1720.96 L1747.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1747.54,1720.96 1747.54,1720.96 1747.82,1720.96 1747.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1747.82 1720.96 L1747.82 1720.96 L1748.11 1720.96 L1748.11 1720.96 L1747.82 1720.96 L1747.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1747.82,1720.96 1747.82,1720.96 1748.11,1720.96 1747.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1748.11 1720.96 L1748.11 1720.96 L1748.39 1720.96 L1748.39 1720.96 L1748.11 1720.96 L1748.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1748.11,1720.96 1748.11,1720.96 1748.39,1720.96 1748.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1748.39 1720.96 L1748.39 1720.96 L1748.67 1720.96 L1748.67 1720.96 L1748.39 1720.96 L1748.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1748.39,1720.96 1748.39,1720.96 1748.67,1720.96 1748.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1748.67 1720.96 L1748.67 1720.96 L1748.95 1720.96 L1748.95 1720.96 L1748.67 1720.96 L1748.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1748.67,1720.96 1748.67,1720.96 1748.95,1720.96 1748.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1748.95 1720.96 L1748.95 1720.96 L1749.23 1720.96 L1749.23 1720.96 L1748.95 1720.96 L1748.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1748.95,1720.96 1748.95,1720.96 1749.23,1720.96 1748.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1749.23 1720.96 L1749.23 1720.96 L1749.51 1720.96 L1749.51 1720.96 L1749.23 1720.96 L1749.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1749.23,1720.96 1749.23,1720.96 1749.51,1720.96 1749.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1749.51 1720.96 L1749.51 1720.96 L1749.8 1720.96 L1749.8 1720.96 L1749.51 1720.96 L1749.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1749.51,1720.96 1749.51,1720.96 1749.8,1720.96 1749.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1749.8 1720.96 L1749.8 1720.96 L1750.08 1720.96 L1750.08 1720.96 L1749.8 1720.96 L1749.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1749.8,1720.96 1749.8,1720.96 1750.08,1720.96 1749.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1750.08 1720.96 L1750.08 1720.96 L1750.36 1720.96 L1750.36 1720.96 L1750.08 1720.96 L1750.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1750.08,1720.96 1750.08,1720.96 1750.36,1720.96 1750.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1750.36 1720.96 L1750.36 1720.96 L1750.64 1720.96 L1750.64 1720.96 L1750.36 1720.96 L1750.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1750.36,1720.96 1750.36,1720.96 1750.64,1720.96 1750.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1750.64 1720.96 L1750.64 1720.96 L1750.92 1720.96 L1750.92 1720.96 L1750.64 1720.96 L1750.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1750.64,1720.96 1750.64,1720.96 1750.92,1720.96 1750.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1750.92 1720.96 L1750.92 1720.96 L1751.2 1720.96 L1751.2 1720.96 L1750.92 1720.96 L1750.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1750.92,1720.96 1750.92,1720.96 1751.2,1720.96 1750.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1751.2 1720.96 L1751.2 1720.96 L1751.49 1720.96 L1751.49 1720.96 L1751.2 1720.96 L1751.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1751.2,1720.96 1751.2,1720.96 1751.49,1720.96 1751.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1751.49 1720.96 L1751.49 1720.96 L1751.77 1720.96 L1751.77 1720.96 L1751.49 1720.96 L1751.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1751.49,1720.96 1751.49,1720.96 1751.77,1720.96 1751.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1751.77 1720.96 L1751.77 1720.96 L1752.05 1720.96 L1752.05 1720.96 L1751.77 1720.96 L1751.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1751.77,1720.96 1751.77,1720.96 1752.05,1720.96 1751.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1752.05 1720.96 L1752.05 1720.96 L1752.33 1720.96 L1752.33 1720.96 L1752.05 1720.96 L1752.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1752.05,1720.96 1752.05,1720.96 1752.33,1720.96 1752.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1752.33 1720.96 L1752.33 1720.96 L1752.61 1720.96 L1752.61 1720.96 L1752.33 1720.96 L1752.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1752.33,1720.96 1752.33,1720.96 1752.61,1720.96 1752.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1752.61 1720.96 L1752.61 1720.96 L1752.89 1720.96 L1752.89 1720.96 L1752.61 1720.96 L1752.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1752.61,1720.96 1752.61,1720.96 1752.89,1720.96 1752.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1752.89 1720.96 L1752.89 1720.96 L1753.18 1720.96 L1753.18 1720.96 L1752.89 1720.96 L1752.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1752.89,1720.96 1752.89,1720.96 1753.18,1720.96 1752.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1753.18 1720.96 L1753.18 1720.96 L1753.46 1720.96 L1753.46 1720.96 L1753.18 1720.96 L1753.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1753.18,1720.96 1753.18,1720.96 1753.46,1720.96 1753.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1753.46 1720.76 L1753.46 1720.96 L1753.74 1720.96 L1753.74 1720.76 L1753.46 1720.76 L1753.46 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1753.46,1720.76 1753.46,1720.96 1753.74,1720.96 1753.74,1720.76 1753.46,1720.76 "/>
<path clip-path="url(#clip322)" d="M1753.74 1720.96 L1753.74 1720.96 L1754.02 1720.96 L1754.02 1720.96 L1753.74 1720.96 L1753.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1753.74,1720.96 1753.74,1720.96 1754.02,1720.96 1753.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1754.02 1720.96 L1754.02 1720.96 L1754.3 1720.96 L1754.3 1720.96 L1754.02 1720.96 L1754.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1754.02,1720.96 1754.02,1720.96 1754.3,1720.96 1754.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1754.3 1720.96 L1754.3 1720.96 L1754.58 1720.96 L1754.58 1720.96 L1754.3 1720.96 L1754.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1754.3,1720.96 1754.3,1720.96 1754.58,1720.96 1754.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1754.58 1720.96 L1754.58 1720.96 L1754.87 1720.96 L1754.87 1720.96 L1754.58 1720.96 L1754.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1754.58,1720.96 1754.58,1720.96 1754.87,1720.96 1754.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1754.87 1720.96 L1754.87 1720.96 L1755.15 1720.96 L1755.15 1720.96 L1754.87 1720.96 L1754.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1754.87,1720.96 1754.87,1720.96 1755.15,1720.96 1754.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1755.15 1720.96 L1755.15 1720.96 L1755.43 1720.96 L1755.43 1720.96 L1755.15 1720.96 L1755.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1755.15,1720.96 1755.15,1720.96 1755.43,1720.96 1755.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1755.43 1720.96 L1755.43 1720.96 L1755.71 1720.96 L1755.71 1720.96 L1755.43 1720.96 L1755.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1755.43,1720.96 1755.43,1720.96 1755.71,1720.96 1755.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1755.71 1720.96 L1755.71 1720.96 L1755.99 1720.96 L1755.99 1720.96 L1755.71 1720.96 L1755.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1755.71,1720.96 1755.71,1720.96 1755.99,1720.96 1755.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1755.99 1720.96 L1755.99 1720.96 L1756.28 1720.96 L1756.28 1720.96 L1755.99 1720.96 L1755.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1755.99,1720.96 1755.99,1720.96 1756.28,1720.96 1755.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1756.28 1720.96 L1756.28 1720.96 L1756.56 1720.96 L1756.56 1720.96 L1756.28 1720.96 L1756.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1756.28,1720.96 1756.28,1720.96 1756.56,1720.96 1756.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1756.56 1720.96 L1756.56 1720.96 L1756.84 1720.96 L1756.84 1720.96 L1756.56 1720.96 L1756.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1756.56,1720.96 1756.56,1720.96 1756.84,1720.96 1756.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1756.84 1720.96 L1756.84 1720.96 L1757.12 1720.96 L1757.12 1720.96 L1756.84 1720.96 L1756.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1756.84,1720.96 1756.84,1720.96 1757.12,1720.96 1756.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1757.12 1720.96 L1757.12 1720.96 L1757.4 1720.96 L1757.4 1720.96 L1757.12 1720.96 L1757.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1757.12,1720.96 1757.12,1720.96 1757.4,1720.96 1757.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1757.4 1720.96 L1757.4 1720.96 L1757.68 1720.96 L1757.68 1720.96 L1757.4 1720.96 L1757.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1757.4,1720.96 1757.4,1720.96 1757.68,1720.96 1757.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1757.68 1720.96 L1757.68 1720.96 L1757.97 1720.96 L1757.97 1720.96 L1757.68 1720.96 L1757.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1757.68,1720.96 1757.68,1720.96 1757.97,1720.96 1757.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1757.97 1720.96 L1757.97 1720.96 L1758.25 1720.96 L1758.25 1720.96 L1757.97 1720.96 L1757.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1757.97,1720.96 1757.97,1720.96 1758.25,1720.96 1757.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1758.25 1720.96 L1758.25 1720.96 L1758.53 1720.96 L1758.53 1720.96 L1758.25 1720.96 L1758.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1758.25,1720.96 1758.25,1720.96 1758.53,1720.96 1758.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1758.53 1720.96 L1758.53 1720.96 L1758.81 1720.96 L1758.81 1720.96 L1758.53 1720.96 L1758.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1758.53,1720.96 1758.53,1720.96 1758.81,1720.96 1758.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1758.81 1720.96 L1758.81 1720.96 L1759.09 1720.96 L1759.09 1720.96 L1758.81 1720.96 L1758.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1758.81,1720.96 1758.81,1720.96 1759.09,1720.96 1758.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1759.09 1720.96 L1759.09 1720.96 L1759.37 1720.96 L1759.37 1720.96 L1759.09 1720.96 L1759.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1759.09,1720.96 1759.09,1720.96 1759.37,1720.96 1759.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1759.37 1720.96 L1759.37 1720.96 L1759.66 1720.96 L1759.66 1720.96 L1759.37 1720.96 L1759.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1759.37,1720.96 1759.37,1720.96 1759.66,1720.96 1759.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1759.66 1720.96 L1759.66 1720.96 L1759.94 1720.96 L1759.94 1720.96 L1759.66 1720.96 L1759.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1759.66,1720.96 1759.66,1720.96 1759.94,1720.96 1759.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1759.94 1720.96 L1759.94 1720.96 L1760.22 1720.96 L1760.22 1720.96 L1759.94 1720.96 L1759.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1759.94,1720.96 1759.94,1720.96 1760.22,1720.96 1759.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1760.22 1720.96 L1760.22 1720.96 L1760.5 1720.96 L1760.5 1720.96 L1760.22 1720.96 L1760.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1760.22,1720.96 1760.22,1720.96 1760.5,1720.96 1760.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1760.5 1720.96 L1760.5 1720.96 L1760.78 1720.96 L1760.78 1720.96 L1760.5 1720.96 L1760.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1760.5,1720.96 1760.5,1720.96 1760.78,1720.96 1760.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1760.78 1720.96 L1760.78 1720.96 L1761.06 1720.96 L1761.06 1720.96 L1760.78 1720.96 L1760.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1760.78,1720.96 1760.78,1720.96 1761.06,1720.96 1760.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1761.06 1720.96 L1761.06 1720.96 L1761.35 1720.96 L1761.35 1720.96 L1761.06 1720.96 L1761.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1761.06,1720.96 1761.06,1720.96 1761.35,1720.96 1761.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1761.35 1720.96 L1761.35 1720.96 L1761.63 1720.96 L1761.63 1720.96 L1761.35 1720.96 L1761.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1761.35,1720.96 1761.35,1720.96 1761.63,1720.96 1761.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1761.63 1720.96 L1761.63 1720.96 L1761.91 1720.96 L1761.91 1720.96 L1761.63 1720.96 L1761.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1761.63,1720.96 1761.63,1720.96 1761.91,1720.96 1761.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1761.91 1720.96 L1761.91 1720.96 L1762.19 1720.96 L1762.19 1720.96 L1761.91 1720.96 L1761.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1761.91,1720.96 1761.91,1720.96 1762.19,1720.96 1761.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1762.19 1720.96 L1762.19 1720.96 L1762.47 1720.96 L1762.47 1720.96 L1762.19 1720.96 L1762.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1762.19,1720.96 1762.19,1720.96 1762.47,1720.96 1762.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1762.47 1720.96 L1762.47 1720.96 L1762.75 1720.96 L1762.75 1720.96 L1762.47 1720.96 L1762.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1762.47,1720.96 1762.47,1720.96 1762.75,1720.96 1762.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1762.75 1720.96 L1762.75 1720.96 L1763.04 1720.96 L1763.04 1720.96 L1762.75 1720.96 L1762.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1762.75,1720.96 1762.75,1720.96 1763.04,1720.96 1762.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1763.04 1720.96 L1763.04 1720.96 L1763.32 1720.96 L1763.32 1720.96 L1763.04 1720.96 L1763.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1763.04,1720.96 1763.04,1720.96 1763.32,1720.96 1763.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1763.32 1720.96 L1763.32 1720.96 L1763.6 1720.96 L1763.6 1720.96 L1763.32 1720.96 L1763.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1763.32,1720.96 1763.32,1720.96 1763.6,1720.96 1763.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1763.6 1720.96 L1763.6 1720.96 L1763.88 1720.96 L1763.88 1720.96 L1763.6 1720.96 L1763.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1763.6,1720.96 1763.6,1720.96 1763.88,1720.96 1763.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1763.88 1720.96 L1763.88 1720.96 L1764.16 1720.96 L1764.16 1720.96 L1763.88 1720.96 L1763.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1763.88,1720.96 1763.88,1720.96 1764.16,1720.96 1763.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1764.16 1720.96 L1764.16 1720.96 L1764.45 1720.96 L1764.45 1720.96 L1764.16 1720.96 L1764.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1764.16,1720.96 1764.16,1720.96 1764.45,1720.96 1764.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1764.45 1720.96 L1764.45 1720.96 L1764.73 1720.96 L1764.73 1720.96 L1764.45 1720.96 L1764.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1764.45,1720.96 1764.45,1720.96 1764.73,1720.96 1764.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1764.73 1720.96 L1764.73 1720.96 L1765.01 1720.96 L1765.01 1720.96 L1764.73 1720.96 L1764.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1764.73,1720.96 1764.73,1720.96 1765.01,1720.96 1764.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1765.01 1720.96 L1765.01 1720.96 L1765.29 1720.96 L1765.29 1720.96 L1765.01 1720.96 L1765.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1765.01,1720.96 1765.01,1720.96 1765.29,1720.96 1765.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1765.29 1720.96 L1765.29 1720.96 L1765.57 1720.96 L1765.57 1720.96 L1765.29 1720.96 L1765.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1765.29,1720.96 1765.29,1720.96 1765.57,1720.96 1765.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1765.57 1720.96 L1765.57 1720.96 L1765.85 1720.96 L1765.85 1720.96 L1765.57 1720.96 L1765.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1765.57,1720.96 1765.57,1720.96 1765.85,1720.96 1765.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1765.85 1720.96 L1765.85 1720.96 L1766.14 1720.96 L1766.14 1720.96 L1765.85 1720.96 L1765.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1765.85,1720.96 1765.85,1720.96 1766.14,1720.96 1765.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1766.14 1720.96 L1766.14 1720.96 L1766.42 1720.96 L1766.42 1720.96 L1766.14 1720.96 L1766.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1766.14,1720.96 1766.14,1720.96 1766.42,1720.96 1766.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1766.42 1720.96 L1766.42 1720.96 L1766.7 1720.96 L1766.7 1720.96 L1766.42 1720.96 L1766.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1766.42,1720.96 1766.42,1720.96 1766.7,1720.96 1766.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1766.7 1720.96 L1766.7 1720.96 L1766.98 1720.96 L1766.98 1720.96 L1766.7 1720.96 L1766.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1766.7,1720.96 1766.7,1720.96 1766.98,1720.96 1766.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1766.98 1720.96 L1766.98 1720.96 L1767.26 1720.96 L1767.26 1720.96 L1766.98 1720.96 L1766.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1766.98,1720.96 1766.98,1720.96 1767.26,1720.96 1766.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1767.26 1720.96 L1767.26 1720.96 L1767.54 1720.96 L1767.54 1720.96 L1767.26 1720.96 L1767.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1767.26,1720.96 1767.26,1720.96 1767.54,1720.96 1767.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1767.54 1720.96 L1767.54 1720.96 L1767.83 1720.96 L1767.83 1720.96 L1767.54 1720.96 L1767.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1767.54,1720.96 1767.54,1720.96 1767.83,1720.96 1767.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1767.83 1720.96 L1767.83 1720.96 L1768.11 1720.96 L1768.11 1720.96 L1767.83 1720.96 L1767.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1767.83,1720.96 1767.83,1720.96 1768.11,1720.96 1767.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1768.11 1720.96 L1768.11 1720.96 L1768.39 1720.96 L1768.39 1720.96 L1768.11 1720.96 L1768.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1768.11,1720.96 1768.11,1720.96 1768.39,1720.96 1768.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1768.39 1720.96 L1768.39 1720.96 L1768.67 1720.96 L1768.67 1720.96 L1768.39 1720.96 L1768.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1768.39,1720.96 1768.39,1720.96 1768.67,1720.96 1768.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1768.67 1720.96 L1768.67 1720.96 L1768.95 1720.96 L1768.95 1720.96 L1768.67 1720.96 L1768.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1768.67,1720.96 1768.67,1720.96 1768.95,1720.96 1768.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1768.95 1720.96 L1768.95 1720.96 L1769.23 1720.96 L1769.23 1720.96 L1768.95 1720.96 L1768.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1768.95,1720.96 1768.95,1720.96 1769.23,1720.96 1768.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1769.23 1720.96 L1769.23 1720.96 L1769.52 1720.96 L1769.52 1720.96 L1769.23 1720.96 L1769.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1769.23,1720.96 1769.23,1720.96 1769.52,1720.96 1769.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1769.52 1720.96 L1769.52 1720.96 L1769.8 1720.96 L1769.8 1720.96 L1769.52 1720.96 L1769.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1769.52,1720.96 1769.52,1720.96 1769.8,1720.96 1769.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1769.8 1720.96 L1769.8 1720.96 L1770.08 1720.96 L1770.08 1720.96 L1769.8 1720.96 L1769.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1769.8,1720.96 1769.8,1720.96 1770.08,1720.96 1769.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1770.08 1720.96 L1770.08 1720.96 L1770.36 1720.96 L1770.36 1720.96 L1770.08 1720.96 L1770.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1770.08,1720.96 1770.08,1720.96 1770.36,1720.96 1770.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1770.36 1720.96 L1770.36 1720.96 L1770.64 1720.96 L1770.64 1720.96 L1770.36 1720.96 L1770.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1770.36,1720.96 1770.36,1720.96 1770.64,1720.96 1770.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1770.64 1720.96 L1770.64 1720.96 L1770.92 1720.96 L1770.92 1720.96 L1770.64 1720.96 L1770.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1770.64,1720.96 1770.64,1720.96 1770.92,1720.96 1770.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1770.92 1720.96 L1770.92 1720.96 L1771.21 1720.96 L1771.21 1720.96 L1770.92 1720.96 L1770.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1770.92,1720.96 1770.92,1720.96 1771.21,1720.96 1770.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1771.21 1720.96 L1771.21 1720.96 L1771.49 1720.96 L1771.49 1720.96 L1771.21 1720.96 L1771.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1771.21,1720.96 1771.21,1720.96 1771.49,1720.96 1771.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1771.49 1720.96 L1771.49 1720.96 L1771.77 1720.96 L1771.77 1720.96 L1771.49 1720.96 L1771.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1771.49,1720.96 1771.49,1720.96 1771.77,1720.96 1771.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1771.77 1720.96 L1771.77 1720.96 L1772.05 1720.96 L1772.05 1720.96 L1771.77 1720.96 L1771.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1771.77,1720.96 1771.77,1720.96 1772.05,1720.96 1771.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1772.05 1720.96 L1772.05 1720.96 L1772.33 1720.96 L1772.33 1720.96 L1772.05 1720.96 L1772.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1772.05,1720.96 1772.05,1720.96 1772.33,1720.96 1772.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1772.33 1720.96 L1772.33 1720.96 L1772.62 1720.96 L1772.62 1720.96 L1772.33 1720.96 L1772.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1772.33,1720.96 1772.33,1720.96 1772.62,1720.96 1772.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1772.62 1720.96 L1772.62 1720.96 L1772.9 1720.96 L1772.9 1720.96 L1772.62 1720.96 L1772.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1772.62,1720.96 1772.62,1720.96 1772.9,1720.96 1772.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1772.9 1720.96 L1772.9 1720.96 L1773.18 1720.96 L1773.18 1720.96 L1772.9 1720.96 L1772.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1772.9,1720.96 1772.9,1720.96 1773.18,1720.96 1772.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1773.18 1720.96 L1773.18 1720.96 L1773.46 1720.96 L1773.46 1720.96 L1773.18 1720.96 L1773.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1773.18,1720.96 1773.18,1720.96 1773.46,1720.96 1773.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1773.46 1720.96 L1773.46 1720.96 L1773.74 1720.96 L1773.74 1720.96 L1773.46 1720.96 L1773.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1773.46,1720.96 1773.46,1720.96 1773.74,1720.96 1773.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1773.74 1720.96 L1773.74 1720.96 L1774.02 1720.96 L1774.02 1720.96 L1773.74 1720.96 L1773.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1773.74,1720.96 1773.74,1720.96 1774.02,1720.96 1773.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1774.02 1720.96 L1774.02 1720.96 L1774.31 1720.96 L1774.31 1720.96 L1774.02 1720.96 L1774.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1774.02,1720.96 1774.02,1720.96 1774.31,1720.96 1774.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1774.31 1720.96 L1774.31 1720.96 L1774.59 1720.96 L1774.59 1720.96 L1774.31 1720.96 L1774.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1774.31,1720.96 1774.31,1720.96 1774.59,1720.96 1774.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1774.59 1720.96 L1774.59 1720.96 L1774.87 1720.96 L1774.87 1720.96 L1774.59 1720.96 L1774.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1774.59,1720.96 1774.59,1720.96 1774.87,1720.96 1774.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1774.87 1720.96 L1774.87 1720.96 L1775.15 1720.96 L1775.15 1720.96 L1774.87 1720.96 L1774.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1774.87,1720.96 1774.87,1720.96 1775.15,1720.96 1774.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1775.15 1720.96 L1775.15 1720.96 L1775.43 1720.96 L1775.43 1720.96 L1775.15 1720.96 L1775.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1775.15,1720.96 1775.15,1720.96 1775.43,1720.96 1775.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1775.43 1720.96 L1775.43 1720.96 L1775.71 1720.96 L1775.71 1720.96 L1775.43 1720.96 L1775.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1775.43,1720.96 1775.43,1720.96 1775.71,1720.96 1775.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1775.71 1720.96 L1775.71 1720.96 L1776 1720.96 L1776 1720.96 L1775.71 1720.96 L1775.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1775.71,1720.96 1775.71,1720.96 1776,1720.96 1775.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1776 1720.96 L1776 1720.96 L1776.28 1720.96 L1776.28 1720.96 L1776 1720.96 L1776 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1776,1720.96 1776,1720.96 1776.28,1720.96 1776,1720.96 "/>
<path clip-path="url(#clip322)" d="M1776.28 1720.96 L1776.28 1720.96 L1776.56 1720.96 L1776.56 1720.96 L1776.28 1720.96 L1776.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1776.28,1720.96 1776.28,1720.96 1776.56,1720.96 1776.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1776.56 1720.96 L1776.56 1720.96 L1776.84 1720.96 L1776.84 1720.96 L1776.56 1720.96 L1776.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1776.56,1720.96 1776.56,1720.96 1776.84,1720.96 1776.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1776.84 1720.96 L1776.84 1720.96 L1777.12 1720.96 L1777.12 1720.96 L1776.84 1720.96 L1776.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1776.84,1720.96 1776.84,1720.96 1777.12,1720.96 1776.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1777.12 1720.96 L1777.12 1720.96 L1777.4 1720.96 L1777.4 1720.96 L1777.12 1720.96 L1777.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1777.12,1720.96 1777.12,1720.96 1777.4,1720.96 1777.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1777.4 1720.96 L1777.4 1720.96 L1777.69 1720.96 L1777.69 1720.96 L1777.4 1720.96 L1777.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1777.4,1720.96 1777.4,1720.96 1777.69,1720.96 1777.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1777.69 1720.96 L1777.69 1720.96 L1777.97 1720.96 L1777.97 1720.96 L1777.69 1720.96 L1777.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1777.69,1720.96 1777.69,1720.96 1777.97,1720.96 1777.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1777.97 1720.96 L1777.97 1720.96 L1778.25 1720.96 L1778.25 1720.96 L1777.97 1720.96 L1777.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1777.97,1720.96 1777.97,1720.96 1778.25,1720.96 1777.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1778.25 1720.96 L1778.25 1720.96 L1778.53 1720.96 L1778.53 1720.96 L1778.25 1720.96 L1778.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1778.25,1720.96 1778.25,1720.96 1778.53,1720.96 1778.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1778.53 1720.96 L1778.53 1720.96 L1778.81 1720.96 L1778.81 1720.96 L1778.53 1720.96 L1778.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1778.53,1720.96 1778.53,1720.96 1778.81,1720.96 1778.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1778.81 1720.96 L1778.81 1720.96 L1779.09 1720.96 L1779.09 1720.96 L1778.81 1720.96 L1778.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1778.81,1720.96 1778.81,1720.96 1779.09,1720.96 1778.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1779.09 1720.96 L1779.09 1720.96 L1779.38 1720.96 L1779.38 1720.96 L1779.09 1720.96 L1779.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1779.09,1720.96 1779.09,1720.96 1779.38,1720.96 1779.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1779.38 1720.96 L1779.38 1720.96 L1779.66 1720.96 L1779.66 1720.96 L1779.38 1720.96 L1779.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1779.38,1720.96 1779.38,1720.96 1779.66,1720.96 1779.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1779.66 1720.96 L1779.66 1720.96 L1779.94 1720.96 L1779.94 1720.96 L1779.66 1720.96 L1779.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1779.66,1720.96 1779.66,1720.96 1779.94,1720.96 1779.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1779.94 1720.96 L1779.94 1720.96 L1780.22 1720.96 L1780.22 1720.96 L1779.94 1720.96 L1779.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1779.94,1720.96 1779.94,1720.96 1780.22,1720.96 1779.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1780.22 1720.96 L1780.22 1720.96 L1780.5 1720.96 L1780.5 1720.96 L1780.22 1720.96 L1780.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1780.22,1720.96 1780.22,1720.96 1780.5,1720.96 1780.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1780.5 1720.96 L1780.5 1720.96 L1780.79 1720.96 L1780.79 1720.96 L1780.5 1720.96 L1780.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1780.5,1720.96 1780.5,1720.96 1780.79,1720.96 1780.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1780.79 1720.96 L1780.79 1720.96 L1781.07 1720.96 L1781.07 1720.96 L1780.79 1720.96 L1780.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1780.79,1720.96 1780.79,1720.96 1781.07,1720.96 1780.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1781.07 1720.96 L1781.07 1720.96 L1781.35 1720.96 L1781.35 1720.96 L1781.07 1720.96 L1781.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1781.07,1720.96 1781.07,1720.96 1781.35,1720.96 1781.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1781.35 1720.96 L1781.35 1720.96 L1781.63 1720.96 L1781.63 1720.96 L1781.35 1720.96 L1781.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1781.35,1720.96 1781.35,1720.96 1781.63,1720.96 1781.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1781.63 1720.96 L1781.63 1720.96 L1781.91 1720.96 L1781.91 1720.96 L1781.63 1720.96 L1781.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1781.63,1720.96 1781.63,1720.96 1781.91,1720.96 1781.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1781.91 1720.96 L1781.91 1720.96 L1782.19 1720.96 L1782.19 1720.96 L1781.91 1720.96 L1781.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1781.91,1720.96 1781.91,1720.96 1782.19,1720.96 1781.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1782.19 1720.96 L1782.19 1720.96 L1782.48 1720.96 L1782.48 1720.96 L1782.19 1720.96 L1782.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1782.19,1720.96 1782.19,1720.96 1782.48,1720.96 1782.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1782.48 1720.96 L1782.48 1720.96 L1782.76 1720.96 L1782.76 1720.96 L1782.48 1720.96 L1782.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1782.48,1720.96 1782.48,1720.96 1782.76,1720.96 1782.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1782.76 1720.96 L1782.76 1720.96 L1783.04 1720.96 L1783.04 1720.96 L1782.76 1720.96 L1782.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1782.76,1720.96 1782.76,1720.96 1783.04,1720.96 1782.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1783.04 1720.96 L1783.04 1720.96 L1783.32 1720.96 L1783.32 1720.96 L1783.04 1720.96 L1783.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1783.04,1720.96 1783.04,1720.96 1783.32,1720.96 1783.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1783.32 1720.96 L1783.32 1720.96 L1783.6 1720.96 L1783.6 1720.96 L1783.32 1720.96 L1783.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1783.32,1720.96 1783.32,1720.96 1783.6,1720.96 1783.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1783.6 1720.96 L1783.6 1720.96 L1783.88 1720.96 L1783.88 1720.96 L1783.6 1720.96 L1783.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1783.6,1720.96 1783.6,1720.96 1783.88,1720.96 1783.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1783.88 1720.96 L1783.88 1720.96 L1784.17 1720.96 L1784.17 1720.96 L1783.88 1720.96 L1783.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1783.88,1720.96 1783.88,1720.96 1784.17,1720.96 1783.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1784.17 1720.96 L1784.17 1720.96 L1784.45 1720.96 L1784.45 1720.96 L1784.17 1720.96 L1784.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1784.17,1720.96 1784.17,1720.96 1784.45,1720.96 1784.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1784.45 1720.96 L1784.45 1720.96 L1784.73 1720.96 L1784.73 1720.96 L1784.45 1720.96 L1784.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1784.45,1720.96 1784.45,1720.96 1784.73,1720.96 1784.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1784.73 1720.96 L1784.73 1720.96 L1785.01 1720.96 L1785.01 1720.96 L1784.73 1720.96 L1784.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1784.73,1720.96 1784.73,1720.96 1785.01,1720.96 1784.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1785.01 1720.96 L1785.01 1720.96 L1785.29 1720.96 L1785.29 1720.96 L1785.01 1720.96 L1785.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1785.01,1720.96 1785.01,1720.96 1785.29,1720.96 1785.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1785.29 1720.96 L1785.29 1720.96 L1785.57 1720.96 L1785.57 1720.96 L1785.29 1720.96 L1785.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1785.29,1720.96 1785.29,1720.96 1785.57,1720.96 1785.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1785.57 1720.96 L1785.57 1720.96 L1785.86 1720.96 L1785.86 1720.96 L1785.57 1720.96 L1785.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1785.57,1720.96 1785.57,1720.96 1785.86,1720.96 1785.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1785.86 1720.96 L1785.86 1720.96 L1786.14 1720.96 L1786.14 1720.96 L1785.86 1720.96 L1785.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1785.86,1720.96 1785.86,1720.96 1786.14,1720.96 1785.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1786.14 1720.96 L1786.14 1720.96 L1786.42 1720.96 L1786.42 1720.96 L1786.14 1720.96 L1786.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1786.14,1720.96 1786.14,1720.96 1786.42,1720.96 1786.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1786.42 1720.96 L1786.42 1720.96 L1786.7 1720.96 L1786.7 1720.96 L1786.42 1720.96 L1786.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1786.42,1720.96 1786.42,1720.96 1786.7,1720.96 1786.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1786.7 1720.96 L1786.7 1720.96 L1786.98 1720.96 L1786.98 1720.96 L1786.7 1720.96 L1786.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1786.7,1720.96 1786.7,1720.96 1786.98,1720.96 1786.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1786.98 1720.96 L1786.98 1720.96 L1787.27 1720.96 L1787.27 1720.96 L1786.98 1720.96 L1786.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1786.98,1720.96 1786.98,1720.96 1787.27,1720.96 1786.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1787.27 1720.96 L1787.27 1720.96 L1787.55 1720.96 L1787.55 1720.96 L1787.27 1720.96 L1787.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1787.27,1720.96 1787.27,1720.96 1787.55,1720.96 1787.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1787.55 1720.96 L1787.55 1720.96 L1787.83 1720.96 L1787.83 1720.96 L1787.55 1720.96 L1787.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1787.55,1720.96 1787.55,1720.96 1787.83,1720.96 1787.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1787.83 1720.96 L1787.83 1720.96 L1788.11 1720.96 L1788.11 1720.96 L1787.83 1720.96 L1787.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1787.83,1720.96 1787.83,1720.96 1788.11,1720.96 1787.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1788.11 1720.96 L1788.11 1720.96 L1788.39 1720.96 L1788.39 1720.96 L1788.11 1720.96 L1788.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1788.11,1720.96 1788.11,1720.96 1788.39,1720.96 1788.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1788.39 1720.96 L1788.39 1720.96 L1788.67 1720.96 L1788.67 1720.96 L1788.39 1720.96 L1788.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1788.39,1720.96 1788.39,1720.96 1788.67,1720.96 1788.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1788.67 1720.96 L1788.67 1720.96 L1788.96 1720.96 L1788.96 1720.96 L1788.67 1720.96 L1788.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1788.67,1720.96 1788.67,1720.96 1788.96,1720.96 1788.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1788.96 1720.96 L1788.96 1720.96 L1789.24 1720.96 L1789.24 1720.96 L1788.96 1720.96 L1788.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1788.96,1720.96 1788.96,1720.96 1789.24,1720.96 1788.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1789.24 1720.96 L1789.24 1720.96 L1789.52 1720.96 L1789.52 1720.96 L1789.24 1720.96 L1789.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1789.24,1720.96 1789.24,1720.96 1789.52,1720.96 1789.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1789.52 1720.96 L1789.52 1720.96 L1789.8 1720.96 L1789.8 1720.96 L1789.52 1720.96 L1789.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1789.52,1720.96 1789.52,1720.96 1789.8,1720.96 1789.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1789.8 1720.96 L1789.8 1720.96 L1790.08 1720.96 L1790.08 1720.96 L1789.8 1720.96 L1789.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1789.8,1720.96 1789.8,1720.96 1790.08,1720.96 1789.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1790.08 1720.96 L1790.08 1720.96 L1790.36 1720.96 L1790.36 1720.96 L1790.08 1720.96 L1790.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1790.08,1720.96 1790.08,1720.96 1790.36,1720.96 1790.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1790.36 1720.96 L1790.36 1720.96 L1790.65 1720.96 L1790.65 1720.96 L1790.36 1720.96 L1790.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1790.36,1720.96 1790.36,1720.96 1790.65,1720.96 1790.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1790.65 1720.96 L1790.65 1720.96 L1790.93 1720.96 L1790.93 1720.96 L1790.65 1720.96 L1790.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1790.65,1720.96 1790.65,1720.96 1790.93,1720.96 1790.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1790.93 1720.96 L1790.93 1720.96 L1791.21 1720.96 L1791.21 1720.96 L1790.93 1720.96 L1790.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1790.93,1720.96 1790.93,1720.96 1791.21,1720.96 1790.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1791.21 1720.96 L1791.21 1720.96 L1791.49 1720.96 L1791.49 1720.96 L1791.21 1720.96 L1791.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1791.21,1720.96 1791.21,1720.96 1791.49,1720.96 1791.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1791.49 1720.96 L1791.49 1720.96 L1791.77 1720.96 L1791.77 1720.96 L1791.49 1720.96 L1791.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1791.49,1720.96 1791.49,1720.96 1791.77,1720.96 1791.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1791.77 1720.96 L1791.77 1720.96 L1792.05 1720.96 L1792.05 1720.96 L1791.77 1720.96 L1791.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1791.77,1720.96 1791.77,1720.96 1792.05,1720.96 1791.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1792.05 1720.96 L1792.05 1720.96 L1792.34 1720.96 L1792.34 1720.96 L1792.05 1720.96 L1792.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1792.05,1720.96 1792.05,1720.96 1792.34,1720.96 1792.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1792.34 1720.96 L1792.34 1720.96 L1792.62 1720.96 L1792.62 1720.96 L1792.34 1720.96 L1792.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1792.34,1720.96 1792.34,1720.96 1792.62,1720.96 1792.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1792.62 1720.96 L1792.62 1720.96 L1792.9 1720.96 L1792.9 1720.96 L1792.62 1720.96 L1792.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1792.62,1720.96 1792.62,1720.96 1792.9,1720.96 1792.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1792.9 1720.96 L1792.9 1720.96 L1793.18 1720.96 L1793.18 1720.96 L1792.9 1720.96 L1792.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1792.9,1720.96 1792.9,1720.96 1793.18,1720.96 1792.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1793.18 1720.96 L1793.18 1720.96 L1793.46 1720.96 L1793.46 1720.96 L1793.18 1720.96 L1793.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1793.18,1720.96 1793.18,1720.96 1793.46,1720.96 1793.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1793.46 1720.96 L1793.46 1720.96 L1793.74 1720.96 L1793.74 1720.96 L1793.46 1720.96 L1793.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1793.46,1720.96 1793.46,1720.96 1793.74,1720.96 1793.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1793.74 1720.96 L1793.74 1720.96 L1794.03 1720.96 L1794.03 1720.96 L1793.74 1720.96 L1793.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1793.74,1720.96 1793.74,1720.96 1794.03,1720.96 1793.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1794.03 1720.96 L1794.03 1720.96 L1794.31 1720.96 L1794.31 1720.96 L1794.03 1720.96 L1794.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1794.03,1720.96 1794.03,1720.96 1794.31,1720.96 1794.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1794.31 1720.96 L1794.31 1720.96 L1794.59 1720.96 L1794.59 1720.96 L1794.31 1720.96 L1794.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1794.31,1720.96 1794.31,1720.96 1794.59,1720.96 1794.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1794.59 1720.96 L1794.59 1720.96 L1794.87 1720.96 L1794.87 1720.96 L1794.59 1720.96 L1794.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1794.59,1720.96 1794.59,1720.96 1794.87,1720.96 1794.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1794.87 1720.96 L1794.87 1720.96 L1795.15 1720.96 L1795.15 1720.96 L1794.87 1720.96 L1794.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1794.87,1720.96 1794.87,1720.96 1795.15,1720.96 1794.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1795.15 1720.96 L1795.15 1720.96 L1795.44 1720.96 L1795.44 1720.96 L1795.15 1720.96 L1795.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1795.15,1720.96 1795.15,1720.96 1795.44,1720.96 1795.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1795.44 1720.96 L1795.44 1720.96 L1795.72 1720.96 L1795.72 1720.96 L1795.44 1720.96 L1795.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1795.44,1720.96 1795.44,1720.96 1795.72,1720.96 1795.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1795.72 1720.96 L1795.72 1720.96 L1796 1720.96 L1796 1720.96 L1795.72 1720.96 L1795.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1795.72,1720.96 1795.72,1720.96 1796,1720.96 1795.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1796 1720.96 L1796 1720.96 L1796.28 1720.96 L1796.28 1720.96 L1796 1720.96 L1796 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1796,1720.96 1796,1720.96 1796.28,1720.96 1796,1720.96 "/>
<path clip-path="url(#clip322)" d="M1796.28 1720.96 L1796.28 1720.96 L1796.56 1720.96 L1796.56 1720.96 L1796.28 1720.96 L1796.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1796.28,1720.96 1796.28,1720.96 1796.56,1720.96 1796.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1796.56 1720.96 L1796.56 1720.96 L1796.84 1720.96 L1796.84 1720.96 L1796.56 1720.96 L1796.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1796.56,1720.96 1796.56,1720.96 1796.84,1720.96 1796.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1796.84 1720.96 L1796.84 1720.96 L1797.13 1720.96 L1797.13 1720.96 L1796.84 1720.96 L1796.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1796.84,1720.96 1796.84,1720.96 1797.13,1720.96 1796.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1797.13 1720.96 L1797.13 1720.96 L1797.41 1720.96 L1797.41 1720.96 L1797.13 1720.96 L1797.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1797.13,1720.96 1797.13,1720.96 1797.41,1720.96 1797.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1797.41 1720.96 L1797.41 1720.96 L1797.69 1720.96 L1797.69 1720.96 L1797.41 1720.96 L1797.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1797.41,1720.96 1797.41,1720.96 1797.69,1720.96 1797.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1797.69 1720.96 L1797.69 1720.96 L1797.97 1720.96 L1797.97 1720.96 L1797.69 1720.96 L1797.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1797.69,1720.96 1797.69,1720.96 1797.97,1720.96 1797.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1797.97 1720.96 L1797.97 1720.96 L1798.25 1720.96 L1798.25 1720.96 L1797.97 1720.96 L1797.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1797.97,1720.96 1797.97,1720.96 1798.25,1720.96 1797.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1798.25 1720.96 L1798.25 1720.96 L1798.53 1720.96 L1798.53 1720.96 L1798.25 1720.96 L1798.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1798.25,1720.96 1798.25,1720.96 1798.53,1720.96 1798.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1798.53 1720.96 L1798.53 1720.96 L1798.82 1720.96 L1798.82 1720.96 L1798.53 1720.96 L1798.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1798.53,1720.96 1798.53,1720.96 1798.82,1720.96 1798.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1798.82 1720.96 L1798.82 1720.96 L1799.1 1720.96 L1799.1 1720.96 L1798.82 1720.96 L1798.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1798.82,1720.96 1798.82,1720.96 1799.1,1720.96 1798.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1799.1 1720.96 L1799.1 1720.96 L1799.38 1720.96 L1799.38 1720.96 L1799.1 1720.96 L1799.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1799.1,1720.96 1799.1,1720.96 1799.38,1720.96 1799.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1799.38 1720.96 L1799.38 1720.96 L1799.66 1720.96 L1799.66 1720.96 L1799.38 1720.96 L1799.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1799.38,1720.96 1799.38,1720.96 1799.66,1720.96 1799.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1799.66 1720.96 L1799.66 1720.96 L1799.94 1720.96 L1799.94 1720.96 L1799.66 1720.96 L1799.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1799.66,1720.96 1799.66,1720.96 1799.94,1720.96 1799.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1799.94 1720.96 L1799.94 1720.96 L1800.22 1720.96 L1800.22 1720.96 L1799.94 1720.96 L1799.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1799.94,1720.96 1799.94,1720.96 1800.22,1720.96 1799.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1800.22 1720.96 L1800.22 1720.96 L1800.51 1720.96 L1800.51 1720.96 L1800.22 1720.96 L1800.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1800.22,1720.96 1800.22,1720.96 1800.51,1720.96 1800.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1800.51 1720.96 L1800.51 1720.96 L1800.79 1720.96 L1800.79 1720.96 L1800.51 1720.96 L1800.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1800.51,1720.96 1800.51,1720.96 1800.79,1720.96 1800.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1800.79 1720.96 L1800.79 1720.96 L1801.07 1720.96 L1801.07 1720.96 L1800.79 1720.96 L1800.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1800.79,1720.96 1800.79,1720.96 1801.07,1720.96 1800.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1801.07 1720.96 L1801.07 1720.96 L1801.35 1720.96 L1801.35 1720.96 L1801.07 1720.96 L1801.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1801.07,1720.96 1801.07,1720.96 1801.35,1720.96 1801.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1801.35 1720.96 L1801.35 1720.96 L1801.63 1720.96 L1801.63 1720.96 L1801.35 1720.96 L1801.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1801.35,1720.96 1801.35,1720.96 1801.63,1720.96 1801.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1801.63 1720.96 L1801.63 1720.96 L1801.91 1720.96 L1801.91 1720.96 L1801.63 1720.96 L1801.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1801.63,1720.96 1801.63,1720.96 1801.91,1720.96 1801.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1801.91 1720.96 L1801.91 1720.96 L1802.2 1720.96 L1802.2 1720.96 L1801.91 1720.96 L1801.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1801.91,1720.96 1801.91,1720.96 1802.2,1720.96 1801.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1802.2 1720.96 L1802.2 1720.96 L1802.48 1720.96 L1802.48 1720.96 L1802.2 1720.96 L1802.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1802.2,1720.96 1802.2,1720.96 1802.48,1720.96 1802.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1802.48 1720.96 L1802.48 1720.96 L1802.76 1720.96 L1802.76 1720.96 L1802.48 1720.96 L1802.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1802.48,1720.96 1802.48,1720.96 1802.76,1720.96 1802.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1802.76 1720.96 L1802.76 1720.96 L1803.04 1720.96 L1803.04 1720.96 L1802.76 1720.96 L1802.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1802.76,1720.96 1802.76,1720.96 1803.04,1720.96 1802.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1803.04 1720.96 L1803.04 1720.96 L1803.32 1720.96 L1803.32 1720.96 L1803.04 1720.96 L1803.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1803.04,1720.96 1803.04,1720.96 1803.32,1720.96 1803.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1803.32 1720.96 L1803.32 1720.96 L1803.61 1720.96 L1803.61 1720.96 L1803.32 1720.96 L1803.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1803.32,1720.96 1803.32,1720.96 1803.61,1720.96 1803.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1803.61 1720.96 L1803.61 1720.96 L1803.89 1720.96 L1803.89 1720.96 L1803.61 1720.96 L1803.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1803.61,1720.96 1803.61,1720.96 1803.89,1720.96 1803.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1803.89 1720.96 L1803.89 1720.96 L1804.17 1720.96 L1804.17 1720.96 L1803.89 1720.96 L1803.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1803.89,1720.96 1803.89,1720.96 1804.17,1720.96 1803.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1804.17 1720.96 L1804.17 1720.96 L1804.45 1720.96 L1804.45 1720.96 L1804.17 1720.96 L1804.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1804.17,1720.96 1804.17,1720.96 1804.45,1720.96 1804.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1804.45 1720.96 L1804.45 1720.96 L1804.73 1720.96 L1804.73 1720.96 L1804.45 1720.96 L1804.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1804.45,1720.96 1804.45,1720.96 1804.73,1720.96 1804.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1804.73 1720.96 L1804.73 1720.96 L1805.01 1720.96 L1805.01 1720.96 L1804.73 1720.96 L1804.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1804.73,1720.96 1804.73,1720.96 1805.01,1720.96 1804.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1805.01 1720.96 L1805.01 1720.96 L1805.3 1720.96 L1805.3 1720.96 L1805.01 1720.96 L1805.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1805.01,1720.96 1805.01,1720.96 1805.3,1720.96 1805.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1805.3 1720.96 L1805.3 1720.96 L1805.58 1720.96 L1805.58 1720.96 L1805.3 1720.96 L1805.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1805.3,1720.96 1805.3,1720.96 1805.58,1720.96 1805.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1805.58 1720.96 L1805.58 1720.96 L1805.86 1720.96 L1805.86 1720.96 L1805.58 1720.96 L1805.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1805.58,1720.96 1805.58,1720.96 1805.86,1720.96 1805.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1805.86 1720.96 L1805.86 1720.96 L1806.14 1720.96 L1806.14 1720.96 L1805.86 1720.96 L1805.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1805.86,1720.96 1805.86,1720.96 1806.14,1720.96 1805.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1806.14 1720.96 L1806.14 1720.96 L1806.42 1720.96 L1806.42 1720.96 L1806.14 1720.96 L1806.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1806.14,1720.96 1806.14,1720.96 1806.42,1720.96 1806.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1806.42 1720.96 L1806.42 1720.96 L1806.7 1720.96 L1806.7 1720.96 L1806.42 1720.96 L1806.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1806.42,1720.96 1806.42,1720.96 1806.7,1720.96 1806.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1806.7 1720.96 L1806.7 1720.96 L1806.99 1720.96 L1806.99 1720.96 L1806.7 1720.96 L1806.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1806.7,1720.96 1806.7,1720.96 1806.99,1720.96 1806.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1806.99 1720.96 L1806.99 1720.96 L1807.27 1720.96 L1807.27 1720.96 L1806.99 1720.96 L1806.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1806.99,1720.96 1806.99,1720.96 1807.27,1720.96 1806.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1807.27 1720.96 L1807.27 1720.96 L1807.55 1720.96 L1807.55 1720.96 L1807.27 1720.96 L1807.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1807.27,1720.96 1807.27,1720.96 1807.55,1720.96 1807.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1807.55 1720.96 L1807.55 1720.96 L1807.83 1720.96 L1807.83 1720.96 L1807.55 1720.96 L1807.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1807.55,1720.96 1807.55,1720.96 1807.83,1720.96 1807.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1807.83 1720.96 L1807.83 1720.96 L1808.11 1720.96 L1808.11 1720.96 L1807.83 1720.96 L1807.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1807.83,1720.96 1807.83,1720.96 1808.11,1720.96 1807.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1808.11 1720.96 L1808.11 1720.96 L1808.39 1720.96 L1808.39 1720.96 L1808.11 1720.96 L1808.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1808.11,1720.96 1808.11,1720.96 1808.39,1720.96 1808.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1808.39 1720.96 L1808.39 1720.96 L1808.68 1720.96 L1808.68 1720.96 L1808.39 1720.96 L1808.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1808.39,1720.96 1808.39,1720.96 1808.68,1720.96 1808.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1808.68 1720.96 L1808.68 1720.96 L1808.96 1720.96 L1808.96 1720.96 L1808.68 1720.96 L1808.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1808.68,1720.96 1808.68,1720.96 1808.96,1720.96 1808.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1808.96 1720.96 L1808.96 1720.96 L1809.24 1720.96 L1809.24 1720.96 L1808.96 1720.96 L1808.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1808.96,1720.96 1808.96,1720.96 1809.24,1720.96 1808.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1809.24 1720.96 L1809.24 1720.96 L1809.52 1720.96 L1809.52 1720.96 L1809.24 1720.96 L1809.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1809.24,1720.96 1809.24,1720.96 1809.52,1720.96 1809.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1809.52 1720.96 L1809.52 1720.96 L1809.8 1720.96 L1809.8 1720.96 L1809.52 1720.96 L1809.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1809.52,1720.96 1809.52,1720.96 1809.8,1720.96 1809.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1809.8 1720.96 L1809.8 1720.96 L1810.08 1720.96 L1810.08 1720.96 L1809.8 1720.96 L1809.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1809.8,1720.96 1809.8,1720.96 1810.08,1720.96 1809.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1810.08 1720.96 L1810.08 1720.96 L1810.37 1720.96 L1810.37 1720.96 L1810.08 1720.96 L1810.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1810.08,1720.96 1810.08,1720.96 1810.37,1720.96 1810.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1810.37 1720.96 L1810.37 1720.96 L1810.65 1720.96 L1810.65 1720.96 L1810.37 1720.96 L1810.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1810.37,1720.96 1810.37,1720.96 1810.65,1720.96 1810.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1810.65 1720.96 L1810.65 1720.96 L1810.93 1720.96 L1810.93 1720.96 L1810.65 1720.96 L1810.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1810.65,1720.96 1810.65,1720.96 1810.93,1720.96 1810.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1810.93 1720.96 L1810.93 1720.96 L1811.21 1720.96 L1811.21 1720.96 L1810.93 1720.96 L1810.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1810.93,1720.96 1810.93,1720.96 1811.21,1720.96 1810.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1811.21 1720.96 L1811.21 1720.96 L1811.49 1720.96 L1811.49 1720.96 L1811.21 1720.96 L1811.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1811.21,1720.96 1811.21,1720.96 1811.49,1720.96 1811.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1811.49 1720.96 L1811.49 1720.96 L1811.78 1720.96 L1811.78 1720.96 L1811.49 1720.96 L1811.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1811.49,1720.96 1811.49,1720.96 1811.78,1720.96 1811.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1811.78 1720.96 L1811.78 1720.96 L1812.06 1720.96 L1812.06 1720.96 L1811.78 1720.96 L1811.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1811.78,1720.96 1811.78,1720.96 1812.06,1720.96 1811.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1812.06 1720.96 L1812.06 1720.96 L1812.34 1720.96 L1812.34 1720.96 L1812.06 1720.96 L1812.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1812.06,1720.96 1812.06,1720.96 1812.34,1720.96 1812.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1812.34 1720.96 L1812.34 1720.96 L1812.62 1720.96 L1812.62 1720.96 L1812.34 1720.96 L1812.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1812.34,1720.96 1812.34,1720.96 1812.62,1720.96 1812.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1812.62 1720.96 L1812.62 1720.96 L1812.9 1720.96 L1812.9 1720.96 L1812.62 1720.96 L1812.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1812.62,1720.96 1812.62,1720.96 1812.9,1720.96 1812.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1812.9 1720.96 L1812.9 1720.96 L1813.18 1720.96 L1813.18 1720.96 L1812.9 1720.96 L1812.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1812.9,1720.96 1812.9,1720.96 1813.18,1720.96 1812.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1813.18 1720.96 L1813.18 1720.96 L1813.47 1720.96 L1813.47 1720.96 L1813.18 1720.96 L1813.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1813.18,1720.96 1813.18,1720.96 1813.47,1720.96 1813.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1813.47 1720.96 L1813.47 1720.96 L1813.75 1720.96 L1813.75 1720.96 L1813.47 1720.96 L1813.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1813.47,1720.96 1813.47,1720.96 1813.75,1720.96 1813.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1813.75 1720.96 L1813.75 1720.96 L1814.03 1720.96 L1814.03 1720.96 L1813.75 1720.96 L1813.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1813.75,1720.96 1813.75,1720.96 1814.03,1720.96 1813.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1814.03 1720.96 L1814.03 1720.96 L1814.31 1720.96 L1814.31 1720.96 L1814.03 1720.96 L1814.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1814.03,1720.96 1814.03,1720.96 1814.31,1720.96 1814.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1814.31 1720.96 L1814.31 1720.96 L1814.59 1720.96 L1814.59 1720.96 L1814.31 1720.96 L1814.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1814.31,1720.96 1814.31,1720.96 1814.59,1720.96 1814.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1814.59 1720.96 L1814.59 1720.96 L1814.87 1720.96 L1814.87 1720.96 L1814.59 1720.96 L1814.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1814.59,1720.96 1814.59,1720.96 1814.87,1720.96 1814.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1814.87 1720.96 L1814.87 1720.96 L1815.16 1720.96 L1815.16 1720.96 L1814.87 1720.96 L1814.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1814.87,1720.96 1814.87,1720.96 1815.16,1720.96 1814.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1815.16 1720.96 L1815.16 1720.96 L1815.44 1720.96 L1815.44 1720.96 L1815.16 1720.96 L1815.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1815.16,1720.96 1815.16,1720.96 1815.44,1720.96 1815.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1815.44 1720.96 L1815.44 1720.96 L1815.72 1720.96 L1815.72 1720.96 L1815.44 1720.96 L1815.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1815.44,1720.96 1815.44,1720.96 1815.72,1720.96 1815.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1815.72 1720.96 L1815.72 1720.96 L1816 1720.96 L1816 1720.96 L1815.72 1720.96 L1815.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1815.72,1720.96 1815.72,1720.96 1816,1720.96 1815.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1816 1720.96 L1816 1720.96 L1816.28 1720.96 L1816.28 1720.96 L1816 1720.96 L1816 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1816,1720.96 1816,1720.96 1816.28,1720.96 1816,1720.96 "/>
<path clip-path="url(#clip322)" d="M1816.28 1720.96 L1816.28 1720.96 L1816.56 1720.96 L1816.56 1720.96 L1816.28 1720.96 L1816.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1816.28,1720.96 1816.28,1720.96 1816.56,1720.96 1816.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1816.56 1720.96 L1816.56 1720.96 L1816.85 1720.96 L1816.85 1720.96 L1816.56 1720.96 L1816.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1816.56,1720.96 1816.56,1720.96 1816.85,1720.96 1816.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1816.85 1720.96 L1816.85 1720.96 L1817.13 1720.96 L1817.13 1720.96 L1816.85 1720.96 L1816.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1816.85,1720.96 1816.85,1720.96 1817.13,1720.96 1816.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1817.13 1720.96 L1817.13 1720.96 L1817.41 1720.96 L1817.41 1720.96 L1817.13 1720.96 L1817.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1817.13,1720.96 1817.13,1720.96 1817.41,1720.96 1817.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1817.41 1720.96 L1817.41 1720.96 L1817.69 1720.96 L1817.69 1720.96 L1817.41 1720.96 L1817.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1817.41,1720.96 1817.41,1720.96 1817.69,1720.96 1817.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1817.69 1720.96 L1817.69 1720.96 L1817.97 1720.96 L1817.97 1720.96 L1817.69 1720.96 L1817.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1817.69,1720.96 1817.69,1720.96 1817.97,1720.96 1817.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1817.97 1720.96 L1817.97 1720.96 L1818.25 1720.96 L1818.25 1720.96 L1817.97 1720.96 L1817.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1817.97,1720.96 1817.97,1720.96 1818.25,1720.96 1817.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1818.25 1720.96 L1818.25 1720.96 L1818.54 1720.96 L1818.54 1720.96 L1818.25 1720.96 L1818.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1818.25,1720.96 1818.25,1720.96 1818.54,1720.96 1818.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1818.54 1720.96 L1818.54 1720.96 L1818.82 1720.96 L1818.82 1720.96 L1818.54 1720.96 L1818.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1818.54,1720.96 1818.54,1720.96 1818.82,1720.96 1818.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1818.82 1720.96 L1818.82 1720.96 L1819.1 1720.96 L1819.1 1720.96 L1818.82 1720.96 L1818.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1818.82,1720.96 1818.82,1720.96 1819.1,1720.96 1818.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1819.1 1720.96 L1819.1 1720.96 L1819.38 1720.96 L1819.38 1720.96 L1819.1 1720.96 L1819.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1819.1,1720.96 1819.1,1720.96 1819.38,1720.96 1819.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1819.38 1720.96 L1819.38 1720.96 L1819.66 1720.96 L1819.66 1720.96 L1819.38 1720.96 L1819.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1819.38,1720.96 1819.38,1720.96 1819.66,1720.96 1819.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1819.66 1720.96 L1819.66 1720.96 L1819.95 1720.96 L1819.95 1720.96 L1819.66 1720.96 L1819.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1819.66,1720.96 1819.66,1720.96 1819.95,1720.96 1819.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1819.95 1720.96 L1819.95 1720.96 L1820.23 1720.96 L1820.23 1720.96 L1819.95 1720.96 L1819.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1819.95,1720.96 1819.95,1720.96 1820.23,1720.96 1819.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1820.23 1720.96 L1820.23 1720.96 L1820.51 1720.96 L1820.51 1720.96 L1820.23 1720.96 L1820.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1820.23,1720.96 1820.23,1720.96 1820.51,1720.96 1820.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1820.51 1720.96 L1820.51 1720.96 L1820.79 1720.96 L1820.79 1720.96 L1820.51 1720.96 L1820.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1820.51,1720.96 1820.51,1720.96 1820.79,1720.96 1820.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1820.79 1720.96 L1820.79 1720.96 L1821.07 1720.96 L1821.07 1720.96 L1820.79 1720.96 L1820.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1820.79,1720.96 1820.79,1720.96 1821.07,1720.96 1820.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1821.07 1720.96 L1821.07 1720.96 L1821.35 1720.96 L1821.35 1720.96 L1821.07 1720.96 L1821.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1821.07,1720.96 1821.07,1720.96 1821.35,1720.96 1821.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1821.35 1720.96 L1821.35 1720.96 L1821.64 1720.96 L1821.64 1720.96 L1821.35 1720.96 L1821.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1821.35,1720.96 1821.35,1720.96 1821.64,1720.96 1821.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1821.64 1720.96 L1821.64 1720.96 L1821.92 1720.96 L1821.92 1720.96 L1821.64 1720.96 L1821.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1821.64,1720.96 1821.64,1720.96 1821.92,1720.96 1821.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1821.92 1720.96 L1821.92 1720.96 L1822.2 1720.96 L1822.2 1720.96 L1821.92 1720.96 L1821.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1821.92,1720.96 1821.92,1720.96 1822.2,1720.96 1821.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1822.2 1720.96 L1822.2 1720.96 L1822.48 1720.96 L1822.48 1720.96 L1822.2 1720.96 L1822.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1822.2,1720.96 1822.2,1720.96 1822.48,1720.96 1822.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1822.48 1720.96 L1822.48 1720.96 L1822.76 1720.96 L1822.76 1720.96 L1822.48 1720.96 L1822.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1822.48,1720.96 1822.48,1720.96 1822.76,1720.96 1822.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1822.76 1720.96 L1822.76 1720.96 L1823.04 1720.96 L1823.04 1720.96 L1822.76 1720.96 L1822.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1822.76,1720.96 1822.76,1720.96 1823.04,1720.96 1822.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1823.04 1720.96 L1823.04 1720.96 L1823.33 1720.96 L1823.33 1720.96 L1823.04 1720.96 L1823.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1823.04,1720.96 1823.04,1720.96 1823.33,1720.96 1823.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1823.33 1720.96 L1823.33 1720.96 L1823.61 1720.96 L1823.61 1720.96 L1823.33 1720.96 L1823.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1823.33,1720.96 1823.33,1720.96 1823.61,1720.96 1823.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1823.61 1720.96 L1823.61 1720.96 L1823.89 1720.96 L1823.89 1720.96 L1823.61 1720.96 L1823.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1823.61,1720.96 1823.61,1720.96 1823.89,1720.96 1823.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1823.89 1720.96 L1823.89 1720.96 L1824.17 1720.96 L1824.17 1720.96 L1823.89 1720.96 L1823.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1823.89,1720.96 1823.89,1720.96 1824.17,1720.96 1823.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1824.17 1720.96 L1824.17 1720.96 L1824.45 1720.96 L1824.45 1720.96 L1824.17 1720.96 L1824.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1824.17,1720.96 1824.17,1720.96 1824.45,1720.96 1824.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1824.45 1720.96 L1824.45 1720.96 L1824.73 1720.96 L1824.73 1720.96 L1824.45 1720.96 L1824.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1824.45,1720.96 1824.45,1720.96 1824.73,1720.96 1824.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1824.73 1720.96 L1824.73 1720.96 L1825.02 1720.96 L1825.02 1720.96 L1824.73 1720.96 L1824.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1824.73,1720.96 1824.73,1720.96 1825.02,1720.96 1824.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1825.02 1720.96 L1825.02 1720.96 L1825.3 1720.96 L1825.3 1720.96 L1825.02 1720.96 L1825.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1825.02,1720.96 1825.02,1720.96 1825.3,1720.96 1825.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1825.3 1720.96 L1825.3 1720.96 L1825.58 1720.96 L1825.58 1720.96 L1825.3 1720.96 L1825.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1825.3,1720.96 1825.3,1720.96 1825.58,1720.96 1825.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1825.58 1720.96 L1825.58 1720.96 L1825.86 1720.96 L1825.86 1720.96 L1825.58 1720.96 L1825.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1825.58,1720.96 1825.58,1720.96 1825.86,1720.96 1825.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1825.86 1720.96 L1825.86 1720.96 L1826.14 1720.96 L1826.14 1720.96 L1825.86 1720.96 L1825.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1825.86,1720.96 1825.86,1720.96 1826.14,1720.96 1825.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1826.14 1720.96 L1826.14 1720.96 L1826.42 1720.96 L1826.42 1720.96 L1826.14 1720.96 L1826.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1826.14,1720.96 1826.14,1720.96 1826.42,1720.96 1826.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1826.42 1720.96 L1826.42 1720.96 L1826.71 1720.96 L1826.71 1720.96 L1826.42 1720.96 L1826.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1826.42,1720.96 1826.42,1720.96 1826.71,1720.96 1826.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1826.71 1720.96 L1826.71 1720.96 L1826.99 1720.96 L1826.99 1720.96 L1826.71 1720.96 L1826.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1826.71,1720.96 1826.71,1720.96 1826.99,1720.96 1826.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1826.99 1720.96 L1826.99 1720.96 L1827.27 1720.96 L1827.27 1720.96 L1826.99 1720.96 L1826.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1826.99,1720.96 1826.99,1720.96 1827.27,1720.96 1826.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1827.27 1720.96 L1827.27 1720.96 L1827.55 1720.96 L1827.55 1720.96 L1827.27 1720.96 L1827.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1827.27,1720.96 1827.27,1720.96 1827.55,1720.96 1827.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1827.55 1720.96 L1827.55 1720.96 L1827.83 1720.96 L1827.83 1720.96 L1827.55 1720.96 L1827.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1827.55,1720.96 1827.55,1720.96 1827.83,1720.96 1827.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1827.83 1720.96 L1827.83 1720.96 L1828.12 1720.96 L1828.12 1720.96 L1827.83 1720.96 L1827.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1827.83,1720.96 1827.83,1720.96 1828.12,1720.96 1827.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1828.12 1720.96 L1828.12 1720.96 L1828.4 1720.96 L1828.4 1720.96 L1828.12 1720.96 L1828.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1828.12,1720.96 1828.12,1720.96 1828.4,1720.96 1828.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1828.4 1720.96 L1828.4 1720.96 L1828.68 1720.96 L1828.68 1720.96 L1828.4 1720.96 L1828.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1828.4,1720.96 1828.4,1720.96 1828.68,1720.96 1828.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1828.68 1720.96 L1828.68 1720.96 L1828.96 1720.96 L1828.96 1720.96 L1828.68 1720.96 L1828.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1828.68,1720.96 1828.68,1720.96 1828.96,1720.96 1828.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1828.96 1720.96 L1828.96 1720.96 L1829.24 1720.96 L1829.24 1720.96 L1828.96 1720.96 L1828.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1828.96,1720.96 1828.96,1720.96 1829.24,1720.96 1828.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1829.24 1720.96 L1829.24 1720.96 L1829.52 1720.96 L1829.52 1720.96 L1829.24 1720.96 L1829.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1829.24,1720.96 1829.24,1720.96 1829.52,1720.96 1829.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1829.52 1720.96 L1829.52 1720.96 L1829.81 1720.96 L1829.81 1720.96 L1829.52 1720.96 L1829.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1829.52,1720.96 1829.52,1720.96 1829.81,1720.96 1829.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1829.81 1720.96 L1829.81 1720.96 L1830.09 1720.96 L1830.09 1720.96 L1829.81 1720.96 L1829.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1829.81,1720.96 1829.81,1720.96 1830.09,1720.96 1829.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1830.09 1720.96 L1830.09 1720.96 L1830.37 1720.96 L1830.37 1720.96 L1830.09 1720.96 L1830.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1830.09,1720.96 1830.09,1720.96 1830.37,1720.96 1830.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1830.37 1720.96 L1830.37 1720.96 L1830.65 1720.96 L1830.65 1720.96 L1830.37 1720.96 L1830.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1830.37,1720.96 1830.37,1720.96 1830.65,1720.96 1830.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1830.65 1720.96 L1830.65 1720.96 L1830.93 1720.96 L1830.93 1720.96 L1830.65 1720.96 L1830.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1830.65,1720.96 1830.65,1720.96 1830.93,1720.96 1830.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1830.93 1720.96 L1830.93 1720.96 L1831.21 1720.96 L1831.21 1720.96 L1830.93 1720.96 L1830.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1830.93,1720.96 1830.93,1720.96 1831.21,1720.96 1830.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1831.21 1720.96 L1831.21 1720.96 L1831.5 1720.96 L1831.5 1720.96 L1831.21 1720.96 L1831.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1831.21,1720.96 1831.21,1720.96 1831.5,1720.96 1831.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1831.5 1720.96 L1831.5 1720.96 L1831.78 1720.96 L1831.78 1720.96 L1831.5 1720.96 L1831.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1831.5,1720.96 1831.5,1720.96 1831.78,1720.96 1831.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1831.78 1720.96 L1831.78 1720.96 L1832.06 1720.96 L1832.06 1720.96 L1831.78 1720.96 L1831.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1831.78,1720.96 1831.78,1720.96 1832.06,1720.96 1831.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1832.06 1720.96 L1832.06 1720.96 L1832.34 1720.96 L1832.34 1720.96 L1832.06 1720.96 L1832.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1832.06,1720.96 1832.06,1720.96 1832.34,1720.96 1832.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1832.34 1720.96 L1832.34 1720.96 L1832.62 1720.96 L1832.62 1720.96 L1832.34 1720.96 L1832.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1832.34,1720.96 1832.34,1720.96 1832.62,1720.96 1832.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1832.62 1720.96 L1832.62 1720.96 L1832.9 1720.96 L1832.9 1720.96 L1832.62 1720.96 L1832.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1832.62,1720.96 1832.62,1720.96 1832.9,1720.96 1832.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1832.9 1720.96 L1832.9 1720.96 L1833.19 1720.96 L1833.19 1720.96 L1832.9 1720.96 L1832.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1832.9,1720.96 1832.9,1720.96 1833.19,1720.96 1832.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1833.19 1720.96 L1833.19 1720.96 L1833.47 1720.96 L1833.47 1720.96 L1833.19 1720.96 L1833.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1833.19,1720.96 1833.19,1720.96 1833.47,1720.96 1833.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1833.47 1720.96 L1833.47 1720.96 L1833.75 1720.96 L1833.75 1720.96 L1833.47 1720.96 L1833.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1833.47,1720.96 1833.47,1720.96 1833.75,1720.96 1833.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1833.75 1720.96 L1833.75 1720.96 L1834.03 1720.96 L1834.03 1720.96 L1833.75 1720.96 L1833.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1833.75,1720.96 1833.75,1720.96 1834.03,1720.96 1833.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1834.03 1720.96 L1834.03 1720.96 L1834.31 1720.96 L1834.31 1720.96 L1834.03 1720.96 L1834.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1834.03,1720.96 1834.03,1720.96 1834.31,1720.96 1834.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1834.31 1720.96 L1834.31 1720.96 L1834.59 1720.96 L1834.59 1720.96 L1834.31 1720.96 L1834.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1834.31,1720.96 1834.31,1720.96 1834.59,1720.96 1834.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1834.59 1720.96 L1834.59 1720.96 L1834.88 1720.96 L1834.88 1720.96 L1834.59 1720.96 L1834.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1834.59,1720.96 1834.59,1720.96 1834.88,1720.96 1834.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1834.88 1720.96 L1834.88 1720.96 L1835.16 1720.96 L1835.16 1720.96 L1834.88 1720.96 L1834.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1834.88,1720.96 1834.88,1720.96 1835.16,1720.96 1834.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1835.16 1720.96 L1835.16 1720.96 L1835.44 1720.96 L1835.44 1720.96 L1835.16 1720.96 L1835.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1835.16,1720.96 1835.16,1720.96 1835.44,1720.96 1835.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1835.44 1720.96 L1835.44 1720.96 L1835.72 1720.96 L1835.72 1720.96 L1835.44 1720.96 L1835.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1835.44,1720.96 1835.44,1720.96 1835.72,1720.96 1835.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1835.72 1720.96 L1835.72 1720.96 L1836 1720.96 L1836 1720.96 L1835.72 1720.96 L1835.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1835.72,1720.96 1835.72,1720.96 1836,1720.96 1835.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1836 1720.96 L1836 1720.96 L1836.29 1720.96 L1836.29 1720.96 L1836 1720.96 L1836 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1836,1720.96 1836,1720.96 1836.29,1720.96 1836,1720.96 "/>
<path clip-path="url(#clip322)" d="M1836.29 1720.96 L1836.29 1720.96 L1836.57 1720.96 L1836.57 1720.96 L1836.29 1720.96 L1836.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1836.29,1720.96 1836.29,1720.96 1836.57,1720.96 1836.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1836.57 1720.96 L1836.57 1720.96 L1836.85 1720.96 L1836.85 1720.96 L1836.57 1720.96 L1836.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1836.57,1720.96 1836.57,1720.96 1836.85,1720.96 1836.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1836.85 1720.96 L1836.85 1720.96 L1837.13 1720.96 L1837.13 1720.96 L1836.85 1720.96 L1836.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1836.85,1720.96 1836.85,1720.96 1837.13,1720.96 1836.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1837.13 1720.96 L1837.13 1720.96 L1837.41 1720.96 L1837.41 1720.96 L1837.13 1720.96 L1837.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1837.13,1720.96 1837.13,1720.96 1837.41,1720.96 1837.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1837.41 1720.96 L1837.41 1720.96 L1837.69 1720.96 L1837.69 1720.96 L1837.41 1720.96 L1837.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1837.41,1720.96 1837.41,1720.96 1837.69,1720.96 1837.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1837.69 1720.96 L1837.69 1720.96 L1837.98 1720.96 L1837.98 1720.96 L1837.69 1720.96 L1837.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1837.69,1720.96 1837.69,1720.96 1837.98,1720.96 1837.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1837.98 1720.96 L1837.98 1720.96 L1838.26 1720.96 L1838.26 1720.96 L1837.98 1720.96 L1837.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1837.98,1720.96 1837.98,1720.96 1838.26,1720.96 1837.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1838.26 1720.96 L1838.26 1720.96 L1838.54 1720.96 L1838.54 1720.96 L1838.26 1720.96 L1838.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1838.26,1720.96 1838.26,1720.96 1838.54,1720.96 1838.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1838.54 1720.96 L1838.54 1720.96 L1838.82 1720.96 L1838.82 1720.96 L1838.54 1720.96 L1838.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1838.54,1720.96 1838.54,1720.96 1838.82,1720.96 1838.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1838.82 1720.96 L1838.82 1720.96 L1839.1 1720.96 L1839.1 1720.96 L1838.82 1720.96 L1838.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1838.82,1720.96 1838.82,1720.96 1839.1,1720.96 1838.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1839.1 1720.96 L1839.1 1720.96 L1839.38 1720.96 L1839.38 1720.96 L1839.1 1720.96 L1839.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1839.1,1720.96 1839.1,1720.96 1839.38,1720.96 1839.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1839.38 1720.96 L1839.38 1720.96 L1839.67 1720.96 L1839.67 1720.96 L1839.38 1720.96 L1839.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1839.38,1720.96 1839.38,1720.96 1839.67,1720.96 1839.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1839.67 1720.96 L1839.67 1720.96 L1839.95 1720.96 L1839.95 1720.96 L1839.67 1720.96 L1839.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1839.67,1720.96 1839.67,1720.96 1839.95,1720.96 1839.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1839.95 1720.96 L1839.95 1720.96 L1840.23 1720.96 L1840.23 1720.96 L1839.95 1720.96 L1839.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1839.95,1720.96 1839.95,1720.96 1840.23,1720.96 1839.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1840.23 1720.96 L1840.23 1720.96 L1840.51 1720.96 L1840.51 1720.96 L1840.23 1720.96 L1840.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1840.23,1720.96 1840.23,1720.96 1840.51,1720.96 1840.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1840.51 1720.96 L1840.51 1720.96 L1840.79 1720.96 L1840.79 1720.96 L1840.51 1720.96 L1840.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1840.51,1720.96 1840.51,1720.96 1840.79,1720.96 1840.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1840.79 1720.96 L1840.79 1720.96 L1841.07 1720.96 L1841.07 1720.96 L1840.79 1720.96 L1840.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1840.79,1720.96 1840.79,1720.96 1841.07,1720.96 1840.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1841.07 1720.96 L1841.07 1720.96 L1841.36 1720.96 L1841.36 1720.96 L1841.07 1720.96 L1841.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1841.07,1720.96 1841.07,1720.96 1841.36,1720.96 1841.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1841.36 1720.96 L1841.36 1720.96 L1841.64 1720.96 L1841.64 1720.96 L1841.36 1720.96 L1841.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1841.36,1720.96 1841.36,1720.96 1841.64,1720.96 1841.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1841.64 1720.96 L1841.64 1720.96 L1841.92 1720.96 L1841.92 1720.96 L1841.64 1720.96 L1841.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1841.64,1720.96 1841.64,1720.96 1841.92,1720.96 1841.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1841.92 1720.96 L1841.92 1720.96 L1842.2 1720.96 L1842.2 1720.96 L1841.92 1720.96 L1841.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1841.92,1720.96 1841.92,1720.96 1842.2,1720.96 1841.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1842.2 1720.96 L1842.2 1720.96 L1842.48 1720.96 L1842.48 1720.96 L1842.2 1720.96 L1842.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1842.2,1720.96 1842.2,1720.96 1842.48,1720.96 1842.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1842.48 1720.96 L1842.48 1720.96 L1842.76 1720.96 L1842.76 1720.96 L1842.48 1720.96 L1842.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1842.48,1720.96 1842.48,1720.96 1842.76,1720.96 1842.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1842.76 1720.96 L1842.76 1720.96 L1843.05 1720.96 L1843.05 1720.96 L1842.76 1720.96 L1842.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1842.76,1720.96 1842.76,1720.96 1843.05,1720.96 1842.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1843.05 1720.96 L1843.05 1720.96 L1843.33 1720.96 L1843.33 1720.96 L1843.05 1720.96 L1843.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1843.05,1720.96 1843.05,1720.96 1843.33,1720.96 1843.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1843.33 1720.96 L1843.33 1720.96 L1843.61 1720.96 L1843.61 1720.96 L1843.33 1720.96 L1843.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1843.33,1720.96 1843.33,1720.96 1843.61,1720.96 1843.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1843.61 1720.96 L1843.61 1720.96 L1843.89 1720.96 L1843.89 1720.96 L1843.61 1720.96 L1843.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1843.61,1720.96 1843.61,1720.96 1843.89,1720.96 1843.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1843.89 1720.96 L1843.89 1720.96 L1844.17 1720.96 L1844.17 1720.96 L1843.89 1720.96 L1843.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1843.89,1720.96 1843.89,1720.96 1844.17,1720.96 1843.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1844.17 1720.96 L1844.17 1720.96 L1844.46 1720.96 L1844.46 1720.96 L1844.17 1720.96 L1844.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1844.17,1720.96 1844.17,1720.96 1844.46,1720.96 1844.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1844.46 1720.96 L1844.46 1720.96 L1844.74 1720.96 L1844.74 1720.96 L1844.46 1720.96 L1844.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1844.46,1720.96 1844.46,1720.96 1844.74,1720.96 1844.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1844.74 1720.96 L1844.74 1720.96 L1845.02 1720.96 L1845.02 1720.96 L1844.74 1720.96 L1844.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1844.74,1720.96 1844.74,1720.96 1845.02,1720.96 1844.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1845.02 1720.96 L1845.02 1720.96 L1845.3 1720.96 L1845.3 1720.96 L1845.02 1720.96 L1845.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1845.02,1720.96 1845.02,1720.96 1845.3,1720.96 1845.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1845.3 1720.96 L1845.3 1720.96 L1845.58 1720.96 L1845.58 1720.96 L1845.3 1720.96 L1845.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1845.3,1720.96 1845.3,1720.96 1845.58,1720.96 1845.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1845.58 1720.96 L1845.58 1720.96 L1845.86 1720.96 L1845.86 1720.96 L1845.58 1720.96 L1845.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1845.58,1720.96 1845.58,1720.96 1845.86,1720.96 1845.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1845.86 1720.96 L1845.86 1720.96 L1846.15 1720.96 L1846.15 1720.96 L1845.86 1720.96 L1845.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1845.86,1720.96 1845.86,1720.96 1846.15,1720.96 1845.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1846.15 1720.96 L1846.15 1720.96 L1846.43 1720.96 L1846.43 1720.96 L1846.15 1720.96 L1846.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1846.15,1720.96 1846.15,1720.96 1846.43,1720.96 1846.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1846.43 1720.96 L1846.43 1720.96 L1846.71 1720.96 L1846.71 1720.96 L1846.43 1720.96 L1846.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1846.43,1720.96 1846.43,1720.96 1846.71,1720.96 1846.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1846.71 1720.96 L1846.71 1720.96 L1846.99 1720.96 L1846.99 1720.96 L1846.71 1720.96 L1846.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1846.71,1720.96 1846.71,1720.96 1846.99,1720.96 1846.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1846.99 1720.96 L1846.99 1720.96 L1847.27 1720.96 L1847.27 1720.96 L1846.99 1720.96 L1846.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1846.99,1720.96 1846.99,1720.96 1847.27,1720.96 1846.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1847.27 1720.96 L1847.27 1720.96 L1847.55 1720.96 L1847.55 1720.96 L1847.27 1720.96 L1847.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1847.27,1720.96 1847.27,1720.96 1847.55,1720.96 1847.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1847.55 1720.96 L1847.55 1720.96 L1847.84 1720.96 L1847.84 1720.96 L1847.55 1720.96 L1847.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1847.55,1720.96 1847.55,1720.96 1847.84,1720.96 1847.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1847.84 1720.96 L1847.84 1720.96 L1848.12 1720.96 L1848.12 1720.96 L1847.84 1720.96 L1847.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1847.84,1720.96 1847.84,1720.96 1848.12,1720.96 1847.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1848.12 1720.96 L1848.12 1720.96 L1848.4 1720.96 L1848.4 1720.96 L1848.12 1720.96 L1848.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1848.12,1720.96 1848.12,1720.96 1848.4,1720.96 1848.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1848.4 1720.96 L1848.4 1720.96 L1848.68 1720.96 L1848.68 1720.96 L1848.4 1720.96 L1848.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1848.4,1720.96 1848.4,1720.96 1848.68,1720.96 1848.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1848.68 1720.96 L1848.68 1720.96 L1848.96 1720.96 L1848.96 1720.96 L1848.68 1720.96 L1848.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1848.68,1720.96 1848.68,1720.96 1848.96,1720.96 1848.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1848.96 1720.96 L1848.96 1720.96 L1849.24 1720.96 L1849.24 1720.96 L1848.96 1720.96 L1848.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1848.96,1720.96 1848.96,1720.96 1849.24,1720.96 1848.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1849.24 1720.96 L1849.24 1720.96 L1849.53 1720.96 L1849.53 1720.96 L1849.24 1720.96 L1849.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1849.24,1720.96 1849.24,1720.96 1849.53,1720.96 1849.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1849.53 1720.96 L1849.53 1720.96 L1849.81 1720.96 L1849.81 1720.96 L1849.53 1720.96 L1849.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1849.53,1720.96 1849.53,1720.96 1849.81,1720.96 1849.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1849.81 1720.96 L1849.81 1720.96 L1850.09 1720.96 L1850.09 1720.96 L1849.81 1720.96 L1849.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1849.81,1720.96 1849.81,1720.96 1850.09,1720.96 1849.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1850.09 1720.96 L1850.09 1720.96 L1850.37 1720.96 L1850.37 1720.96 L1850.09 1720.96 L1850.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1850.09,1720.96 1850.09,1720.96 1850.37,1720.96 1850.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1850.37 1720.96 L1850.37 1720.96 L1850.65 1720.96 L1850.65 1720.96 L1850.37 1720.96 L1850.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1850.37,1720.96 1850.37,1720.96 1850.65,1720.96 1850.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1850.65 1720.96 L1850.65 1720.96 L1850.94 1720.96 L1850.94 1720.96 L1850.65 1720.96 L1850.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1850.65,1720.96 1850.65,1720.96 1850.94,1720.96 1850.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1850.94 1720.96 L1850.94 1720.96 L1851.22 1720.96 L1851.22 1720.96 L1850.94 1720.96 L1850.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1850.94,1720.96 1850.94,1720.96 1851.22,1720.96 1850.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1851.22 1720.96 L1851.22 1720.96 L1851.5 1720.96 L1851.5 1720.96 L1851.22 1720.96 L1851.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1851.22,1720.96 1851.22,1720.96 1851.5,1720.96 1851.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1851.5 1720.96 L1851.5 1720.96 L1851.78 1720.96 L1851.78 1720.96 L1851.5 1720.96 L1851.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1851.5,1720.96 1851.5,1720.96 1851.78,1720.96 1851.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1851.78 1720.96 L1851.78 1720.96 L1852.06 1720.96 L1852.06 1720.96 L1851.78 1720.96 L1851.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1851.78,1720.96 1851.78,1720.96 1852.06,1720.96 1851.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1852.06 1720.96 L1852.06 1720.96 L1852.34 1720.96 L1852.34 1720.96 L1852.06 1720.96 L1852.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1852.06,1720.96 1852.06,1720.96 1852.34,1720.96 1852.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1852.34 1720.96 L1852.34 1720.96 L1852.63 1720.96 L1852.63 1720.96 L1852.34 1720.96 L1852.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1852.34,1720.96 1852.34,1720.96 1852.63,1720.96 1852.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1852.63 1720.96 L1852.63 1720.96 L1852.91 1720.96 L1852.91 1720.96 L1852.63 1720.96 L1852.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1852.63,1720.96 1852.63,1720.96 1852.91,1720.96 1852.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1852.91 1720.96 L1852.91 1720.96 L1853.19 1720.96 L1853.19 1720.96 L1852.91 1720.96 L1852.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1852.91,1720.96 1852.91,1720.96 1853.19,1720.96 1852.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1853.19 1720.96 L1853.19 1720.96 L1853.47 1720.96 L1853.47 1720.96 L1853.19 1720.96 L1853.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1853.19,1720.96 1853.19,1720.96 1853.47,1720.96 1853.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1853.47 1720.96 L1853.47 1720.96 L1853.75 1720.96 L1853.75 1720.96 L1853.47 1720.96 L1853.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1853.47,1720.96 1853.47,1720.96 1853.75,1720.96 1853.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1853.75 1720.96 L1853.75 1720.96 L1854.03 1720.96 L1854.03 1720.96 L1853.75 1720.96 L1853.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1853.75,1720.96 1853.75,1720.96 1854.03,1720.96 1853.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1854.03 1720.96 L1854.03 1720.96 L1854.32 1720.96 L1854.32 1720.96 L1854.03 1720.96 L1854.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1854.03,1720.96 1854.03,1720.96 1854.32,1720.96 1854.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1854.32 1720.96 L1854.32 1720.96 L1854.6 1720.96 L1854.6 1720.96 L1854.32 1720.96 L1854.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1854.32,1720.96 1854.32,1720.96 1854.6,1720.96 1854.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1854.6 1720.96 L1854.6 1720.96 L1854.88 1720.96 L1854.88 1720.96 L1854.6 1720.96 L1854.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1854.6,1720.96 1854.6,1720.96 1854.88,1720.96 1854.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1854.88 1720.96 L1854.88 1720.96 L1855.16 1720.96 L1855.16 1720.96 L1854.88 1720.96 L1854.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1854.88,1720.96 1854.88,1720.96 1855.16,1720.96 1854.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1855.16 1720.96 L1855.16 1720.96 L1855.44 1720.96 L1855.44 1720.96 L1855.16 1720.96 L1855.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1855.16,1720.96 1855.16,1720.96 1855.44,1720.96 1855.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1855.44 1720.96 L1855.44 1720.96 L1855.72 1720.96 L1855.72 1720.96 L1855.44 1720.96 L1855.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1855.44,1720.96 1855.44,1720.96 1855.72,1720.96 1855.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1855.72 1720.96 L1855.72 1720.96 L1856.01 1720.96 L1856.01 1720.96 L1855.72 1720.96 L1855.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1855.72,1720.96 1855.72,1720.96 1856.01,1720.96 1855.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1856.01 1720.96 L1856.01 1720.96 L1856.29 1720.96 L1856.29 1720.96 L1856.01 1720.96 L1856.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1856.01,1720.96 1856.01,1720.96 1856.29,1720.96 1856.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1856.29 1720.96 L1856.29 1720.96 L1856.57 1720.96 L1856.57 1720.96 L1856.29 1720.96 L1856.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1856.29,1720.96 1856.29,1720.96 1856.57,1720.96 1856.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1856.57 1720.96 L1856.57 1720.96 L1856.85 1720.96 L1856.85 1720.96 L1856.57 1720.96 L1856.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1856.57,1720.96 1856.57,1720.96 1856.85,1720.96 1856.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1856.85 1720.96 L1856.85 1720.96 L1857.13 1720.96 L1857.13 1720.96 L1856.85 1720.96 L1856.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1856.85,1720.96 1856.85,1720.96 1857.13,1720.96 1856.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1857.13 1720.96 L1857.13 1720.96 L1857.41 1720.96 L1857.41 1720.96 L1857.13 1720.96 L1857.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1857.13,1720.96 1857.13,1720.96 1857.41,1720.96 1857.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1857.41 1720.96 L1857.41 1720.96 L1857.7 1720.96 L1857.7 1720.96 L1857.41 1720.96 L1857.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1857.41,1720.96 1857.41,1720.96 1857.7,1720.96 1857.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1857.7 1720.96 L1857.7 1720.96 L1857.98 1720.96 L1857.98 1720.96 L1857.7 1720.96 L1857.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1857.7,1720.96 1857.7,1720.96 1857.98,1720.96 1857.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1857.98 1720.96 L1857.98 1720.96 L1858.26 1720.96 L1858.26 1720.96 L1857.98 1720.96 L1857.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1857.98,1720.96 1857.98,1720.96 1858.26,1720.96 1857.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1858.26 1720.96 L1858.26 1720.96 L1858.54 1720.96 L1858.54 1720.96 L1858.26 1720.96 L1858.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1858.26,1720.96 1858.26,1720.96 1858.54,1720.96 1858.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1858.54 1720.96 L1858.54 1720.96 L1858.82 1720.96 L1858.82 1720.96 L1858.54 1720.96 L1858.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1858.54,1720.96 1858.54,1720.96 1858.82,1720.96 1858.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1858.82 1720.96 L1858.82 1720.96 L1859.11 1720.96 L1859.11 1720.96 L1858.82 1720.96 L1858.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1858.82,1720.96 1858.82,1720.96 1859.11,1720.96 1858.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1859.11 1720.96 L1859.11 1720.96 L1859.39 1720.96 L1859.39 1720.96 L1859.11 1720.96 L1859.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1859.11,1720.96 1859.11,1720.96 1859.39,1720.96 1859.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1859.39 1720.96 L1859.39 1720.96 L1859.67 1720.96 L1859.67 1720.96 L1859.39 1720.96 L1859.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1859.39,1720.96 1859.39,1720.96 1859.67,1720.96 1859.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1859.67 1720.96 L1859.67 1720.96 L1859.95 1720.96 L1859.95 1720.96 L1859.67 1720.96 L1859.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1859.67,1720.96 1859.67,1720.96 1859.95,1720.96 1859.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1859.95 1720.96 L1859.95 1720.96 L1860.23 1720.96 L1860.23 1720.96 L1859.95 1720.96 L1859.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1859.95,1720.96 1859.95,1720.96 1860.23,1720.96 1859.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1860.23 1720.96 L1860.23 1720.96 L1860.51 1720.96 L1860.51 1720.96 L1860.23 1720.96 L1860.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1860.23,1720.96 1860.23,1720.96 1860.51,1720.96 1860.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1860.51 1720.96 L1860.51 1720.96 L1860.8 1720.96 L1860.8 1720.96 L1860.51 1720.96 L1860.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1860.51,1720.96 1860.51,1720.96 1860.8,1720.96 1860.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1860.8 1720.96 L1860.8 1720.96 L1861.08 1720.96 L1861.08 1720.96 L1860.8 1720.96 L1860.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1860.8,1720.96 1860.8,1720.96 1861.08,1720.96 1860.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1861.08 1720.96 L1861.08 1720.96 L1861.36 1720.96 L1861.36 1720.96 L1861.08 1720.96 L1861.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1861.08,1720.96 1861.08,1720.96 1861.36,1720.96 1861.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1861.36 1720.96 L1861.36 1720.96 L1861.64 1720.96 L1861.64 1720.96 L1861.36 1720.96 L1861.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1861.36,1720.96 1861.36,1720.96 1861.64,1720.96 1861.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1861.64 1720.96 L1861.64 1720.96 L1861.92 1720.96 L1861.92 1720.96 L1861.64 1720.96 L1861.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1861.64,1720.96 1861.64,1720.96 1861.92,1720.96 1861.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1861.92 1720.96 L1861.92 1720.96 L1862.2 1720.96 L1862.2 1720.96 L1861.92 1720.96 L1861.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1861.92,1720.96 1861.92,1720.96 1862.2,1720.96 1861.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1862.2 1720.96 L1862.2 1720.96 L1862.49 1720.96 L1862.49 1720.96 L1862.2 1720.96 L1862.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1862.2,1720.96 1862.2,1720.96 1862.49,1720.96 1862.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1862.49 1720.96 L1862.49 1720.96 L1862.77 1720.96 L1862.77 1720.96 L1862.49 1720.96 L1862.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1862.49,1720.96 1862.49,1720.96 1862.77,1720.96 1862.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1862.77 1720.96 L1862.77 1720.96 L1863.05 1720.96 L1863.05 1720.96 L1862.77 1720.96 L1862.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1862.77,1720.96 1862.77,1720.96 1863.05,1720.96 1862.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1863.05 1720.96 L1863.05 1720.96 L1863.33 1720.96 L1863.33 1720.96 L1863.05 1720.96 L1863.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1863.05,1720.96 1863.05,1720.96 1863.33,1720.96 1863.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1863.33 1720.96 L1863.33 1720.96 L1863.61 1720.96 L1863.61 1720.96 L1863.33 1720.96 L1863.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1863.33,1720.96 1863.33,1720.96 1863.61,1720.96 1863.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1863.61 1720.96 L1863.61 1720.96 L1863.89 1720.96 L1863.89 1720.96 L1863.61 1720.96 L1863.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1863.61,1720.96 1863.61,1720.96 1863.89,1720.96 1863.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1863.89 1720.96 L1863.89 1720.96 L1864.18 1720.96 L1864.18 1720.96 L1863.89 1720.96 L1863.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1863.89,1720.96 1863.89,1720.96 1864.18,1720.96 1863.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1864.18 1720.96 L1864.18 1720.96 L1864.46 1720.96 L1864.46 1720.96 L1864.18 1720.96 L1864.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1864.18,1720.96 1864.18,1720.96 1864.46,1720.96 1864.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1864.46 1720.96 L1864.46 1720.96 L1864.74 1720.96 L1864.74 1720.96 L1864.46 1720.96 L1864.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1864.46,1720.96 1864.46,1720.96 1864.74,1720.96 1864.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1864.74 1720.96 L1864.74 1720.96 L1865.02 1720.96 L1865.02 1720.96 L1864.74 1720.96 L1864.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1864.74,1720.96 1864.74,1720.96 1865.02,1720.96 1864.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1865.02 1720.96 L1865.02 1720.96 L1865.3 1720.96 L1865.3 1720.96 L1865.02 1720.96 L1865.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1865.02,1720.96 1865.02,1720.96 1865.3,1720.96 1865.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1865.3 1720.96 L1865.3 1720.96 L1865.58 1720.96 L1865.58 1720.96 L1865.3 1720.96 L1865.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1865.3,1720.96 1865.3,1720.96 1865.58,1720.96 1865.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1865.58 1720.96 L1865.58 1720.96 L1865.87 1720.96 L1865.87 1720.96 L1865.58 1720.96 L1865.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1865.58,1720.96 1865.58,1720.96 1865.87,1720.96 1865.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1865.87 1720.96 L1865.87 1720.96 L1866.15 1720.96 L1866.15 1720.96 L1865.87 1720.96 L1865.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1865.87,1720.96 1865.87,1720.96 1866.15,1720.96 1865.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1866.15 1720.96 L1866.15 1720.96 L1866.43 1720.96 L1866.43 1720.96 L1866.15 1720.96 L1866.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1866.15,1720.96 1866.15,1720.96 1866.43,1720.96 1866.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1866.43 1720.96 L1866.43 1720.96 L1866.71 1720.96 L1866.71 1720.96 L1866.43 1720.96 L1866.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1866.43,1720.96 1866.43,1720.96 1866.71,1720.96 1866.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1866.71 1720.96 L1866.71 1720.96 L1866.99 1720.96 L1866.99 1720.96 L1866.71 1720.96 L1866.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1866.71,1720.96 1866.71,1720.96 1866.99,1720.96 1866.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1866.99 1720.96 L1866.99 1720.96 L1867.28 1720.96 L1867.28 1720.96 L1866.99 1720.96 L1866.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1866.99,1720.96 1866.99,1720.96 1867.28,1720.96 1866.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1867.28 1720.96 L1867.28 1720.96 L1867.56 1720.96 L1867.56 1720.96 L1867.28 1720.96 L1867.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1867.28,1720.96 1867.28,1720.96 1867.56,1720.96 1867.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1867.56 1720.96 L1867.56 1720.96 L1867.84 1720.96 L1867.84 1720.96 L1867.56 1720.96 L1867.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1867.56,1720.96 1867.56,1720.96 1867.84,1720.96 1867.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1867.84 1720.96 L1867.84 1720.96 L1868.12 1720.96 L1868.12 1720.96 L1867.84 1720.96 L1867.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1867.84,1720.96 1867.84,1720.96 1868.12,1720.96 1867.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1868.12 1720.96 L1868.12 1720.96 L1868.4 1720.96 L1868.4 1720.96 L1868.12 1720.96 L1868.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1868.12,1720.96 1868.12,1720.96 1868.4,1720.96 1868.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1868.4 1720.96 L1868.4 1720.96 L1868.68 1720.96 L1868.68 1720.96 L1868.4 1720.96 L1868.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1868.4,1720.96 1868.4,1720.96 1868.68,1720.96 1868.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1868.68 1720.96 L1868.68 1720.96 L1868.97 1720.96 L1868.97 1720.96 L1868.68 1720.96 L1868.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1868.68,1720.96 1868.68,1720.96 1868.97,1720.96 1868.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1868.97 1720.96 L1868.97 1720.96 L1869.25 1720.96 L1869.25 1720.96 L1868.97 1720.96 L1868.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1868.97,1720.96 1868.97,1720.96 1869.25,1720.96 1868.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1869.25 1720.96 L1869.25 1720.96 L1869.53 1720.96 L1869.53 1720.96 L1869.25 1720.96 L1869.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1869.25,1720.96 1869.25,1720.96 1869.53,1720.96 1869.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1869.53 1720.96 L1869.53 1720.96 L1869.81 1720.96 L1869.81 1720.96 L1869.53 1720.96 L1869.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1869.53,1720.96 1869.53,1720.96 1869.81,1720.96 1869.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1869.81 1720.96 L1869.81 1720.96 L1870.09 1720.96 L1870.09 1720.96 L1869.81 1720.96 L1869.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1869.81,1720.96 1869.81,1720.96 1870.09,1720.96 1869.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1870.09 1720.96 L1870.09 1720.96 L1870.37 1720.96 L1870.37 1720.96 L1870.09 1720.96 L1870.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1870.09,1720.96 1870.09,1720.96 1870.37,1720.96 1870.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1870.37 1720.96 L1870.37 1720.96 L1870.66 1720.96 L1870.66 1720.96 L1870.37 1720.96 L1870.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1870.37,1720.96 1870.37,1720.96 1870.66,1720.96 1870.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1870.66 1720.96 L1870.66 1720.96 L1870.94 1720.96 L1870.94 1720.96 L1870.66 1720.96 L1870.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1870.66,1720.96 1870.66,1720.96 1870.94,1720.96 1870.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1870.94 1720.96 L1870.94 1720.96 L1871.22 1720.96 L1871.22 1720.96 L1870.94 1720.96 L1870.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1870.94,1720.96 1870.94,1720.96 1871.22,1720.96 1870.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1871.22 1720.96 L1871.22 1720.96 L1871.5 1720.96 L1871.5 1720.96 L1871.22 1720.96 L1871.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1871.22,1720.96 1871.22,1720.96 1871.5,1720.96 1871.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1871.5 1720.96 L1871.5 1720.96 L1871.78 1720.96 L1871.78 1720.96 L1871.5 1720.96 L1871.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1871.5,1720.96 1871.5,1720.96 1871.78,1720.96 1871.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1871.78 1720.96 L1871.78 1720.96 L1872.06 1720.96 L1872.06 1720.96 L1871.78 1720.96 L1871.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1871.78,1720.96 1871.78,1720.96 1872.06,1720.96 1871.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1872.06 1720.96 L1872.06 1720.96 L1872.35 1720.96 L1872.35 1720.96 L1872.06 1720.96 L1872.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1872.06,1720.96 1872.06,1720.96 1872.35,1720.96 1872.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1872.35 1720.96 L1872.35 1720.96 L1872.63 1720.96 L1872.63 1720.96 L1872.35 1720.96 L1872.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1872.35,1720.96 1872.35,1720.96 1872.63,1720.96 1872.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1872.63 1720.96 L1872.63 1720.96 L1872.91 1720.96 L1872.91 1720.96 L1872.63 1720.96 L1872.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1872.63,1720.96 1872.63,1720.96 1872.91,1720.96 1872.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1872.91 1720.96 L1872.91 1720.96 L1873.19 1720.96 L1873.19 1720.96 L1872.91 1720.96 L1872.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1872.91,1720.96 1872.91,1720.96 1873.19,1720.96 1872.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1873.19 1720.96 L1873.19 1720.96 L1873.47 1720.96 L1873.47 1720.96 L1873.19 1720.96 L1873.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1873.19,1720.96 1873.19,1720.96 1873.47,1720.96 1873.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1873.47 1720.96 L1873.47 1720.96 L1873.75 1720.96 L1873.75 1720.96 L1873.47 1720.96 L1873.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1873.47,1720.96 1873.47,1720.96 1873.75,1720.96 1873.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1873.75 1720.96 L1873.75 1720.96 L1874.04 1720.96 L1874.04 1720.96 L1873.75 1720.96 L1873.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1873.75,1720.96 1873.75,1720.96 1874.04,1720.96 1873.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1874.04 1720.96 L1874.04 1720.96 L1874.32 1720.96 L1874.32 1720.96 L1874.04 1720.96 L1874.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1874.04,1720.96 1874.04,1720.96 1874.32,1720.96 1874.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1874.32 1720.96 L1874.32 1720.96 L1874.6 1720.96 L1874.6 1720.96 L1874.32 1720.96 L1874.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1874.32,1720.96 1874.32,1720.96 1874.6,1720.96 1874.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1874.6 1720.96 L1874.6 1720.96 L1874.88 1720.96 L1874.88 1720.96 L1874.6 1720.96 L1874.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1874.6,1720.96 1874.6,1720.96 1874.88,1720.96 1874.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1874.88 1720.96 L1874.88 1720.96 L1875.16 1720.96 L1875.16 1720.96 L1874.88 1720.96 L1874.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1874.88,1720.96 1874.88,1720.96 1875.16,1720.96 1874.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1875.16 1720.96 L1875.16 1720.96 L1875.45 1720.96 L1875.45 1720.96 L1875.16 1720.96 L1875.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1875.16,1720.96 1875.16,1720.96 1875.45,1720.96 1875.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1875.45 1720.96 L1875.45 1720.96 L1875.73 1720.96 L1875.73 1720.96 L1875.45 1720.96 L1875.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1875.45,1720.96 1875.45,1720.96 1875.73,1720.96 1875.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1875.73 1720.96 L1875.73 1720.96 L1876.01 1720.96 L1876.01 1720.96 L1875.73 1720.96 L1875.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1875.73,1720.96 1875.73,1720.96 1876.01,1720.96 1875.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1876.01 1720.96 L1876.01 1720.96 L1876.29 1720.96 L1876.29 1720.96 L1876.01 1720.96 L1876.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1876.01,1720.96 1876.01,1720.96 1876.29,1720.96 1876.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1876.29 1720.96 L1876.29 1720.96 L1876.57 1720.96 L1876.57 1720.96 L1876.29 1720.96 L1876.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1876.29,1720.96 1876.29,1720.96 1876.57,1720.96 1876.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1876.57 1720.96 L1876.57 1720.96 L1876.85 1720.96 L1876.85 1720.96 L1876.57 1720.96 L1876.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1876.57,1720.96 1876.57,1720.96 1876.85,1720.96 1876.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1876.85 1720.96 L1876.85 1720.96 L1877.14 1720.96 L1877.14 1720.96 L1876.85 1720.96 L1876.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1876.85,1720.96 1876.85,1720.96 1877.14,1720.96 1876.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1877.14 1720.96 L1877.14 1720.96 L1877.42 1720.96 L1877.42 1720.96 L1877.14 1720.96 L1877.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1877.14,1720.96 1877.14,1720.96 1877.42,1720.96 1877.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1877.42 1720.96 L1877.42 1720.96 L1877.7 1720.96 L1877.7 1720.96 L1877.42 1720.96 L1877.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1877.42,1720.96 1877.42,1720.96 1877.7,1720.96 1877.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1877.7 1720.96 L1877.7 1720.96 L1877.98 1720.96 L1877.98 1720.96 L1877.7 1720.96 L1877.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1877.7,1720.96 1877.7,1720.96 1877.98,1720.96 1877.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1877.98 1720.96 L1877.98 1720.96 L1878.26 1720.96 L1878.26 1720.96 L1877.98 1720.96 L1877.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1877.98,1720.96 1877.98,1720.96 1878.26,1720.96 1877.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1878.26 1720.96 L1878.26 1720.96 L1878.54 1720.96 L1878.54 1720.96 L1878.26 1720.96 L1878.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1878.26,1720.96 1878.26,1720.96 1878.54,1720.96 1878.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1878.54 1720.96 L1878.54 1720.96 L1878.83 1720.96 L1878.83 1720.96 L1878.54 1720.96 L1878.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1878.54,1720.96 1878.54,1720.96 1878.83,1720.96 1878.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1878.83 1720.96 L1878.83 1720.96 L1879.11 1720.96 L1879.11 1720.96 L1878.83 1720.96 L1878.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1878.83,1720.96 1878.83,1720.96 1879.11,1720.96 1878.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1879.11 1720.96 L1879.11 1720.96 L1879.39 1720.96 L1879.39 1720.96 L1879.11 1720.96 L1879.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1879.11,1720.96 1879.11,1720.96 1879.39,1720.96 1879.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1879.39 1720.96 L1879.39 1720.96 L1879.67 1720.96 L1879.67 1720.96 L1879.39 1720.96 L1879.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1879.39,1720.96 1879.39,1720.96 1879.67,1720.96 1879.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1879.67 1720.96 L1879.67 1720.96 L1879.95 1720.96 L1879.95 1720.96 L1879.67 1720.96 L1879.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1879.67,1720.96 1879.67,1720.96 1879.95,1720.96 1879.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1879.95 1720.96 L1879.95 1720.96 L1880.23 1720.96 L1880.23 1720.96 L1879.95 1720.96 L1879.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1879.95,1720.96 1879.95,1720.96 1880.23,1720.96 1879.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1880.23 1720.96 L1880.23 1720.96 L1880.52 1720.96 L1880.52 1720.96 L1880.23 1720.96 L1880.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1880.23,1720.96 1880.23,1720.96 1880.52,1720.96 1880.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1880.52 1720.96 L1880.52 1720.96 L1880.8 1720.96 L1880.8 1720.96 L1880.52 1720.96 L1880.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1880.52,1720.96 1880.52,1720.96 1880.8,1720.96 1880.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1880.8 1720.96 L1880.8 1720.96 L1881.08 1720.96 L1881.08 1720.96 L1880.8 1720.96 L1880.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1880.8,1720.96 1880.8,1720.96 1881.08,1720.96 1880.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1881.08 1720.96 L1881.08 1720.96 L1881.36 1720.96 L1881.36 1720.96 L1881.08 1720.96 L1881.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1881.08,1720.96 1881.08,1720.96 1881.36,1720.96 1881.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1881.36 1720.96 L1881.36 1720.96 L1881.64 1720.96 L1881.64 1720.96 L1881.36 1720.96 L1881.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1881.36,1720.96 1881.36,1720.96 1881.64,1720.96 1881.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1881.64 1720.96 L1881.64 1720.96 L1881.92 1720.96 L1881.92 1720.96 L1881.64 1720.96 L1881.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1881.64,1720.96 1881.64,1720.96 1881.92,1720.96 1881.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1881.92 1720.96 L1881.92 1720.96 L1882.21 1720.96 L1882.21 1720.96 L1881.92 1720.96 L1881.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1881.92,1720.96 1881.92,1720.96 1882.21,1720.96 1881.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1882.21 1720.96 L1882.21 1720.96 L1882.49 1720.96 L1882.49 1720.96 L1882.21 1720.96 L1882.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1882.21,1720.96 1882.21,1720.96 1882.49,1720.96 1882.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1882.49 1720.96 L1882.49 1720.96 L1882.77 1720.96 L1882.77 1720.96 L1882.49 1720.96 L1882.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1882.49,1720.96 1882.49,1720.96 1882.77,1720.96 1882.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1882.77 1720.96 L1882.77 1720.96 L1883.05 1720.96 L1883.05 1720.96 L1882.77 1720.96 L1882.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1882.77,1720.96 1882.77,1720.96 1883.05,1720.96 1882.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1883.05 1720.96 L1883.05 1720.96 L1883.33 1720.96 L1883.33 1720.96 L1883.05 1720.96 L1883.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1883.05,1720.96 1883.05,1720.96 1883.33,1720.96 1883.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1883.33 1720.96 L1883.33 1720.96 L1883.62 1720.96 L1883.62 1720.96 L1883.33 1720.96 L1883.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1883.33,1720.96 1883.33,1720.96 1883.62,1720.96 1883.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1883.62 1720.96 L1883.62 1720.96 L1883.9 1720.96 L1883.9 1720.96 L1883.62 1720.96 L1883.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1883.62,1720.96 1883.62,1720.96 1883.9,1720.96 1883.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1883.9 1720.96 L1883.9 1720.96 L1884.18 1720.96 L1884.18 1720.96 L1883.9 1720.96 L1883.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1883.9,1720.96 1883.9,1720.96 1884.18,1720.96 1883.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1884.18 1720.96 L1884.18 1720.96 L1884.46 1720.96 L1884.46 1720.96 L1884.18 1720.96 L1884.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1884.18,1720.96 1884.18,1720.96 1884.46,1720.96 1884.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1884.46 1720.96 L1884.46 1720.96 L1884.74 1720.96 L1884.74 1720.96 L1884.46 1720.96 L1884.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1884.46,1720.96 1884.46,1720.96 1884.74,1720.96 1884.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1884.74 1720.96 L1884.74 1720.96 L1885.02 1720.96 L1885.02 1720.96 L1884.74 1720.96 L1884.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1884.74,1720.96 1884.74,1720.96 1885.02,1720.96 1884.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1885.02 1720.96 L1885.02 1720.96 L1885.31 1720.96 L1885.31 1720.96 L1885.02 1720.96 L1885.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1885.02,1720.96 1885.02,1720.96 1885.31,1720.96 1885.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1885.31 1720.96 L1885.31 1720.96 L1885.59 1720.96 L1885.59 1720.96 L1885.31 1720.96 L1885.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1885.31,1720.96 1885.31,1720.96 1885.59,1720.96 1885.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1885.59 1720.96 L1885.59 1720.96 L1885.87 1720.96 L1885.87 1720.96 L1885.59 1720.96 L1885.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1885.59,1720.96 1885.59,1720.96 1885.87,1720.96 1885.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1885.87 1720.96 L1885.87 1720.96 L1886.15 1720.96 L1886.15 1720.96 L1885.87 1720.96 L1885.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1885.87,1720.96 1885.87,1720.96 1886.15,1720.96 1885.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1886.15 1720.96 L1886.15 1720.96 L1886.43 1720.96 L1886.43 1720.96 L1886.15 1720.96 L1886.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1886.15,1720.96 1886.15,1720.96 1886.43,1720.96 1886.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1886.43 1720.96 L1886.43 1720.96 L1886.71 1720.96 L1886.71 1720.96 L1886.43 1720.96 L1886.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1886.43,1720.96 1886.43,1720.96 1886.71,1720.96 1886.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1886.71 1720.96 L1886.71 1720.96 L1887 1720.96 L1887 1720.96 L1886.71 1720.96 L1886.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1886.71,1720.96 1886.71,1720.96 1887,1720.96 1886.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1887 1720.96 L1887 1720.96 L1887.28 1720.96 L1887.28 1720.96 L1887 1720.96 L1887 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1887,1720.96 1887,1720.96 1887.28,1720.96 1887,1720.96 "/>
<path clip-path="url(#clip322)" d="M1887.28 1720.96 L1887.28 1720.96 L1887.56 1720.96 L1887.56 1720.96 L1887.28 1720.96 L1887.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1887.28,1720.96 1887.28,1720.96 1887.56,1720.96 1887.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1887.56 1720.96 L1887.56 1720.96 L1887.84 1720.96 L1887.84 1720.96 L1887.56 1720.96 L1887.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1887.56,1720.96 1887.56,1720.96 1887.84,1720.96 1887.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1887.84 1720.96 L1887.84 1720.96 L1888.12 1720.96 L1888.12 1720.96 L1887.84 1720.96 L1887.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1887.84,1720.96 1887.84,1720.96 1888.12,1720.96 1887.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1888.12 1720.96 L1888.12 1720.96 L1888.4 1720.96 L1888.4 1720.96 L1888.12 1720.96 L1888.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1888.12,1720.96 1888.12,1720.96 1888.4,1720.96 1888.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1888.4 1720.96 L1888.4 1720.96 L1888.69 1720.96 L1888.69 1720.96 L1888.4 1720.96 L1888.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1888.4,1720.96 1888.4,1720.96 1888.69,1720.96 1888.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1888.69 1720.96 L1888.69 1720.96 L1888.97 1720.96 L1888.97 1720.96 L1888.69 1720.96 L1888.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1888.69,1720.96 1888.69,1720.96 1888.97,1720.96 1888.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1888.97 1720.96 L1888.97 1720.96 L1889.25 1720.96 L1889.25 1720.96 L1888.97 1720.96 L1888.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1888.97,1720.96 1888.97,1720.96 1889.25,1720.96 1888.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1889.25 1720.96 L1889.25 1720.96 L1889.53 1720.96 L1889.53 1720.96 L1889.25 1720.96 L1889.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1889.25,1720.96 1889.25,1720.96 1889.53,1720.96 1889.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1889.53 1720.96 L1889.53 1720.96 L1889.81 1720.96 L1889.81 1720.96 L1889.53 1720.96 L1889.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1889.53,1720.96 1889.53,1720.96 1889.81,1720.96 1889.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1889.81 1720.96 L1889.81 1720.96 L1890.09 1720.96 L1890.09 1720.96 L1889.81 1720.96 L1889.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1889.81,1720.96 1889.81,1720.96 1890.09,1720.96 1889.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1890.09 1720.96 L1890.09 1720.96 L1890.38 1720.96 L1890.38 1720.96 L1890.09 1720.96 L1890.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1890.09,1720.96 1890.09,1720.96 1890.38,1720.96 1890.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1890.38 1720.96 L1890.38 1720.96 L1890.66 1720.96 L1890.66 1720.96 L1890.38 1720.96 L1890.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1890.38,1720.96 1890.38,1720.96 1890.66,1720.96 1890.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1890.66 1720.96 L1890.66 1720.96 L1890.94 1720.96 L1890.94 1720.96 L1890.66 1720.96 L1890.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1890.66,1720.96 1890.66,1720.96 1890.94,1720.96 1890.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1890.94 1720.96 L1890.94 1720.96 L1891.22 1720.96 L1891.22 1720.96 L1890.94 1720.96 L1890.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1890.94,1720.96 1890.94,1720.96 1891.22,1720.96 1890.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1891.22 1720.96 L1891.22 1720.96 L1891.5 1720.96 L1891.5 1720.96 L1891.22 1720.96 L1891.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1891.22,1720.96 1891.22,1720.96 1891.5,1720.96 1891.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1891.5 1720.96 L1891.5 1720.96 L1891.79 1720.96 L1891.79 1720.96 L1891.5 1720.96 L1891.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1891.5,1720.96 1891.5,1720.96 1891.79,1720.96 1891.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1891.79 1720.96 L1891.79 1720.96 L1892.07 1720.96 L1892.07 1720.96 L1891.79 1720.96 L1891.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1891.79,1720.96 1891.79,1720.96 1892.07,1720.96 1891.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1892.07 1720.96 L1892.07 1720.96 L1892.35 1720.96 L1892.35 1720.96 L1892.07 1720.96 L1892.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1892.07,1720.96 1892.07,1720.96 1892.35,1720.96 1892.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1892.35 1720.96 L1892.35 1720.96 L1892.63 1720.96 L1892.63 1720.96 L1892.35 1720.96 L1892.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1892.35,1720.96 1892.35,1720.96 1892.63,1720.96 1892.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1892.63 1720.96 L1892.63 1720.96 L1892.91 1720.96 L1892.91 1720.96 L1892.63 1720.96 L1892.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1892.63,1720.96 1892.63,1720.96 1892.91,1720.96 1892.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1892.91 1720.96 L1892.91 1720.96 L1893.19 1720.96 L1893.19 1720.96 L1892.91 1720.96 L1892.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1892.91,1720.96 1892.91,1720.96 1893.19,1720.96 1892.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1893.19 1720.96 L1893.19 1720.96 L1893.48 1720.96 L1893.48 1720.96 L1893.19 1720.96 L1893.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1893.19,1720.96 1893.19,1720.96 1893.48,1720.96 1893.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1893.48 1720.96 L1893.48 1720.96 L1893.76 1720.96 L1893.76 1720.96 L1893.48 1720.96 L1893.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1893.48,1720.96 1893.48,1720.96 1893.76,1720.96 1893.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1893.76 1720.96 L1893.76 1720.96 L1894.04 1720.96 L1894.04 1720.96 L1893.76 1720.96 L1893.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1893.76,1720.96 1893.76,1720.96 1894.04,1720.96 1893.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1894.04 1720.96 L1894.04 1720.96 L1894.32 1720.96 L1894.32 1720.96 L1894.04 1720.96 L1894.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1894.04,1720.96 1894.04,1720.96 1894.32,1720.96 1894.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1894.32 1720.96 L1894.32 1720.96 L1894.6 1720.96 L1894.6 1720.96 L1894.32 1720.96 L1894.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1894.32,1720.96 1894.32,1720.96 1894.6,1720.96 1894.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1894.6 1720.96 L1894.6 1720.96 L1894.88 1720.96 L1894.88 1720.96 L1894.6 1720.96 L1894.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1894.6,1720.96 1894.6,1720.96 1894.88,1720.96 1894.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1894.88 1720.96 L1894.88 1720.96 L1895.17 1720.96 L1895.17 1720.96 L1894.88 1720.96 L1894.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1894.88,1720.96 1894.88,1720.96 1895.17,1720.96 1894.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1895.17 1720.96 L1895.17 1720.96 L1895.45 1720.96 L1895.45 1720.96 L1895.17 1720.96 L1895.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1895.17,1720.96 1895.17,1720.96 1895.45,1720.96 1895.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1895.45 1720.96 L1895.45 1720.96 L1895.73 1720.96 L1895.73 1720.96 L1895.45 1720.96 L1895.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1895.45,1720.96 1895.45,1720.96 1895.73,1720.96 1895.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1895.73 1720.96 L1895.73 1720.96 L1896.01 1720.96 L1896.01 1720.96 L1895.73 1720.96 L1895.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1895.73,1720.96 1895.73,1720.96 1896.01,1720.96 1895.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1896.01 1720.96 L1896.01 1720.96 L1896.29 1720.96 L1896.29 1720.96 L1896.01 1720.96 L1896.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1896.01,1720.96 1896.01,1720.96 1896.29,1720.96 1896.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1896.29 1720.96 L1896.29 1720.96 L1896.57 1720.96 L1896.57 1720.96 L1896.29 1720.96 L1896.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1896.29,1720.96 1896.29,1720.96 1896.57,1720.96 1896.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1896.57 1720.96 L1896.57 1720.96 L1896.86 1720.96 L1896.86 1720.96 L1896.57 1720.96 L1896.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1896.57,1720.96 1896.57,1720.96 1896.86,1720.96 1896.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1896.86 1720.96 L1896.86 1720.96 L1897.14 1720.96 L1897.14 1720.96 L1896.86 1720.96 L1896.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1896.86,1720.96 1896.86,1720.96 1897.14,1720.96 1896.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1897.14 1720.96 L1897.14 1720.96 L1897.42 1720.96 L1897.42 1720.96 L1897.14 1720.96 L1897.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1897.14,1720.96 1897.14,1720.96 1897.42,1720.96 1897.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1897.42 1720.96 L1897.42 1720.96 L1897.7 1720.96 L1897.7 1720.96 L1897.42 1720.96 L1897.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1897.42,1720.96 1897.42,1720.96 1897.7,1720.96 1897.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1897.7 1720.96 L1897.7 1720.96 L1897.98 1720.96 L1897.98 1720.96 L1897.7 1720.96 L1897.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1897.7,1720.96 1897.7,1720.96 1897.98,1720.96 1897.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1897.98 1720.96 L1897.98 1720.96 L1898.26 1720.96 L1898.26 1720.96 L1897.98 1720.96 L1897.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1897.98,1720.96 1897.98,1720.96 1898.26,1720.96 1897.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1898.26 1720.96 L1898.26 1720.96 L1898.55 1720.96 L1898.55 1720.96 L1898.26 1720.96 L1898.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1898.26,1720.96 1898.26,1720.96 1898.55,1720.96 1898.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1898.55 1720.96 L1898.55 1720.96 L1898.83 1720.96 L1898.83 1720.96 L1898.55 1720.96 L1898.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1898.55,1720.96 1898.55,1720.96 1898.83,1720.96 1898.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1898.83 1720.96 L1898.83 1720.96 L1899.11 1720.96 L1899.11 1720.96 L1898.83 1720.96 L1898.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1898.83,1720.96 1898.83,1720.96 1899.11,1720.96 1898.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1899.11 1720.96 L1899.11 1720.96 L1899.39 1720.96 L1899.39 1720.96 L1899.11 1720.96 L1899.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1899.11,1720.96 1899.11,1720.96 1899.39,1720.96 1899.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1899.39 1720.96 L1899.39 1720.96 L1899.67 1720.96 L1899.67 1720.96 L1899.39 1720.96 L1899.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1899.39,1720.96 1899.39,1720.96 1899.67,1720.96 1899.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1899.67 1720.96 L1899.67 1720.96 L1899.96 1720.96 L1899.96 1720.96 L1899.67 1720.96 L1899.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1899.67,1720.96 1899.67,1720.96 1899.96,1720.96 1899.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1899.96 1720.96 L1899.96 1720.96 L1900.24 1720.96 L1900.24 1720.96 L1899.96 1720.96 L1899.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1899.96,1720.96 1899.96,1720.96 1900.24,1720.96 1899.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1900.24 1720.96 L1900.24 1720.96 L1900.52 1720.96 L1900.52 1720.96 L1900.24 1720.96 L1900.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1900.24,1720.96 1900.24,1720.96 1900.52,1720.96 1900.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1900.52 1720.96 L1900.52 1720.96 L1900.8 1720.96 L1900.8 1720.96 L1900.52 1720.96 L1900.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1900.52,1720.96 1900.52,1720.96 1900.8,1720.96 1900.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1900.8 1720.96 L1900.8 1720.96 L1901.08 1720.96 L1901.08 1720.96 L1900.8 1720.96 L1900.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1900.8,1720.96 1900.8,1720.96 1901.08,1720.96 1900.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1901.08 1720.96 L1901.08 1720.96 L1901.36 1720.96 L1901.36 1720.96 L1901.08 1720.96 L1901.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1901.08,1720.96 1901.08,1720.96 1901.36,1720.96 1901.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1901.36 1720.96 L1901.36 1720.96 L1901.65 1720.96 L1901.65 1720.96 L1901.36 1720.96 L1901.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1901.36,1720.96 1901.36,1720.96 1901.65,1720.96 1901.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1901.65 1720.96 L1901.65 1720.96 L1901.93 1720.96 L1901.93 1720.96 L1901.65 1720.96 L1901.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1901.65,1720.96 1901.65,1720.96 1901.93,1720.96 1901.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1901.93 1720.96 L1901.93 1720.96 L1902.21 1720.96 L1902.21 1720.96 L1901.93 1720.96 L1901.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1901.93,1720.96 1901.93,1720.96 1902.21,1720.96 1901.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1902.21 1720.96 L1902.21 1720.96 L1902.49 1720.96 L1902.49 1720.96 L1902.21 1720.96 L1902.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1902.21,1720.96 1902.21,1720.96 1902.49,1720.96 1902.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1902.49 1720.96 L1902.49 1720.96 L1902.77 1720.96 L1902.77 1720.96 L1902.49 1720.96 L1902.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1902.49,1720.96 1902.49,1720.96 1902.77,1720.96 1902.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1902.77 1720.96 L1902.77 1720.96 L1903.05 1720.96 L1903.05 1720.96 L1902.77 1720.96 L1902.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1902.77,1720.96 1902.77,1720.96 1903.05,1720.96 1902.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1903.05 1720.96 L1903.05 1720.96 L1903.34 1720.96 L1903.34 1720.96 L1903.05 1720.96 L1903.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1903.05,1720.96 1903.05,1720.96 1903.34,1720.96 1903.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1903.34 1720.96 L1903.34 1720.96 L1903.62 1720.96 L1903.62 1720.96 L1903.34 1720.96 L1903.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1903.34,1720.96 1903.34,1720.96 1903.62,1720.96 1903.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1903.62 1720.96 L1903.62 1720.96 L1903.9 1720.96 L1903.9 1720.96 L1903.62 1720.96 L1903.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1903.62,1720.96 1903.62,1720.96 1903.9,1720.96 1903.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1903.9 1720.96 L1903.9 1720.96 L1904.18 1720.96 L1904.18 1720.96 L1903.9 1720.96 L1903.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1903.9,1720.96 1903.9,1720.96 1904.18,1720.96 1903.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1904.18 1720.96 L1904.18 1720.96 L1904.46 1720.96 L1904.46 1720.96 L1904.18 1720.96 L1904.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1904.18,1720.96 1904.18,1720.96 1904.46,1720.96 1904.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1904.46 1720.96 L1904.46 1720.96 L1904.74 1720.96 L1904.74 1720.96 L1904.46 1720.96 L1904.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1904.46,1720.96 1904.46,1720.96 1904.74,1720.96 1904.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1904.74 1720.96 L1904.74 1720.96 L1905.03 1720.96 L1905.03 1720.96 L1904.74 1720.96 L1904.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1904.74,1720.96 1904.74,1720.96 1905.03,1720.96 1904.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1905.03 1720.96 L1905.03 1720.96 L1905.31 1720.96 L1905.31 1720.96 L1905.03 1720.96 L1905.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1905.03,1720.96 1905.03,1720.96 1905.31,1720.96 1905.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1905.31 1720.96 L1905.31 1720.96 L1905.59 1720.96 L1905.59 1720.96 L1905.31 1720.96 L1905.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1905.31,1720.96 1905.31,1720.96 1905.59,1720.96 1905.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1905.59 1720.96 L1905.59 1720.96 L1905.87 1720.96 L1905.87 1720.96 L1905.59 1720.96 L1905.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1905.59,1720.96 1905.59,1720.96 1905.87,1720.96 1905.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1905.87 1720.96 L1905.87 1720.96 L1906.15 1720.96 L1906.15 1720.96 L1905.87 1720.96 L1905.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1905.87,1720.96 1905.87,1720.96 1906.15,1720.96 1905.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1906.15 1720.96 L1906.15 1720.96 L1906.43 1720.96 L1906.43 1720.96 L1906.15 1720.96 L1906.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1906.15,1720.96 1906.15,1720.96 1906.43,1720.96 1906.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1906.43 1720.96 L1906.43 1720.96 L1906.72 1720.96 L1906.72 1720.96 L1906.43 1720.96 L1906.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1906.43,1720.96 1906.43,1720.96 1906.72,1720.96 1906.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1906.72 1720.96 L1906.72 1720.96 L1907 1720.96 L1907 1720.96 L1906.72 1720.96 L1906.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1906.72,1720.96 1906.72,1720.96 1907,1720.96 1906.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1907 1720.96 L1907 1720.96 L1907.28 1720.96 L1907.28 1720.96 L1907 1720.96 L1907 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1907,1720.96 1907,1720.96 1907.28,1720.96 1907,1720.96 "/>
<path clip-path="url(#clip322)" d="M1907.28 1720.96 L1907.28 1720.96 L1907.56 1720.96 L1907.56 1720.96 L1907.28 1720.96 L1907.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1907.28,1720.96 1907.28,1720.96 1907.56,1720.96 1907.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1907.56 1720.96 L1907.56 1720.96 L1907.84 1720.96 L1907.84 1720.96 L1907.56 1720.96 L1907.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1907.56,1720.96 1907.56,1720.96 1907.84,1720.96 1907.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1907.84 1720.96 L1907.84 1720.96 L1908.13 1720.96 L1908.13 1720.96 L1907.84 1720.96 L1907.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1907.84,1720.96 1907.84,1720.96 1908.13,1720.96 1907.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1908.13 1720.96 L1908.13 1720.96 L1908.41 1720.96 L1908.41 1720.96 L1908.13 1720.96 L1908.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1908.13,1720.96 1908.13,1720.96 1908.41,1720.96 1908.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1908.41 1720.96 L1908.41 1720.96 L1908.69 1720.96 L1908.69 1720.96 L1908.41 1720.96 L1908.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1908.41,1720.96 1908.41,1720.96 1908.69,1720.96 1908.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1908.69 1720.96 L1908.69 1720.96 L1908.97 1720.96 L1908.97 1720.96 L1908.69 1720.96 L1908.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1908.69,1720.96 1908.69,1720.96 1908.97,1720.96 1908.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1908.97 1720.96 L1908.97 1720.96 L1909.25 1720.96 L1909.25 1720.96 L1908.97 1720.96 L1908.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1908.97,1720.96 1908.97,1720.96 1909.25,1720.96 1908.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1909.25 1720.96 L1909.25 1720.96 L1909.53 1720.96 L1909.53 1720.96 L1909.25 1720.96 L1909.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1909.25,1720.96 1909.25,1720.96 1909.53,1720.96 1909.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1909.53 1720.96 L1909.53 1720.96 L1909.82 1720.96 L1909.82 1720.96 L1909.53 1720.96 L1909.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1909.53,1720.96 1909.53,1720.96 1909.82,1720.96 1909.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1909.82 1720.96 L1909.82 1720.96 L1910.1 1720.96 L1910.1 1720.96 L1909.82 1720.96 L1909.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1909.82,1720.96 1909.82,1720.96 1910.1,1720.96 1909.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1910.1 1720.96 L1910.1 1720.96 L1910.38 1720.96 L1910.38 1720.96 L1910.1 1720.96 L1910.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1910.1,1720.96 1910.1,1720.96 1910.38,1720.96 1910.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1910.38 1720.96 L1910.38 1720.96 L1910.66 1720.96 L1910.66 1720.96 L1910.38 1720.96 L1910.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1910.38,1720.96 1910.38,1720.96 1910.66,1720.96 1910.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1910.66 1720.96 L1910.66 1720.96 L1910.94 1720.96 L1910.94 1720.96 L1910.66 1720.96 L1910.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1910.66,1720.96 1910.66,1720.96 1910.94,1720.96 1910.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1910.94 1720.96 L1910.94 1720.96 L1911.22 1720.96 L1911.22 1720.96 L1910.94 1720.96 L1910.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1910.94,1720.96 1910.94,1720.96 1911.22,1720.96 1910.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1911.22 1720.96 L1911.22 1720.96 L1911.51 1720.96 L1911.51 1720.96 L1911.22 1720.96 L1911.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1911.22,1720.96 1911.22,1720.96 1911.51,1720.96 1911.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1911.51 1720.96 L1911.51 1720.96 L1911.79 1720.96 L1911.79 1720.96 L1911.51 1720.96 L1911.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1911.51,1720.96 1911.51,1720.96 1911.79,1720.96 1911.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1911.79 1720.96 L1911.79 1720.96 L1912.07 1720.96 L1912.07 1720.96 L1911.79 1720.96 L1911.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1911.79,1720.96 1911.79,1720.96 1912.07,1720.96 1911.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1912.07 1720.96 L1912.07 1720.96 L1912.35 1720.96 L1912.35 1720.96 L1912.07 1720.96 L1912.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1912.07,1720.96 1912.07,1720.96 1912.35,1720.96 1912.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1912.35 1720.96 L1912.35 1720.96 L1912.63 1720.96 L1912.63 1720.96 L1912.35 1720.96 L1912.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1912.35,1720.96 1912.35,1720.96 1912.63,1720.96 1912.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1912.63 1720.96 L1912.63 1720.96 L1912.91 1720.96 L1912.91 1720.96 L1912.63 1720.96 L1912.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1912.63,1720.96 1912.63,1720.96 1912.91,1720.96 1912.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1912.91 1720.96 L1912.91 1720.96 L1913.2 1720.96 L1913.2 1720.96 L1912.91 1720.96 L1912.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1912.91,1720.96 1912.91,1720.96 1913.2,1720.96 1912.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1913.2 1720.96 L1913.2 1720.96 L1913.48 1720.96 L1913.48 1720.96 L1913.2 1720.96 L1913.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1913.2,1720.96 1913.2,1720.96 1913.48,1720.96 1913.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1913.48 1720.96 L1913.48 1720.96 L1913.76 1720.96 L1913.76 1720.96 L1913.48 1720.96 L1913.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1913.48,1720.96 1913.48,1720.96 1913.76,1720.96 1913.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1913.76 1720.96 L1913.76 1720.96 L1914.04 1720.96 L1914.04 1720.96 L1913.76 1720.96 L1913.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1913.76,1720.96 1913.76,1720.96 1914.04,1720.96 1913.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1914.04 1720.96 L1914.04 1720.96 L1914.32 1720.96 L1914.32 1720.96 L1914.04 1720.96 L1914.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1914.04,1720.96 1914.04,1720.96 1914.32,1720.96 1914.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1914.32 1720.96 L1914.32 1720.96 L1914.61 1720.96 L1914.61 1720.96 L1914.32 1720.96 L1914.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1914.32,1720.96 1914.32,1720.96 1914.61,1720.96 1914.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1914.61 1720.96 L1914.61 1720.96 L1914.89 1720.96 L1914.89 1720.96 L1914.61 1720.96 L1914.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1914.61,1720.96 1914.61,1720.96 1914.89,1720.96 1914.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1914.89 1720.96 L1914.89 1720.96 L1915.17 1720.96 L1915.17 1720.96 L1914.89 1720.96 L1914.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1914.89,1720.96 1914.89,1720.96 1915.17,1720.96 1914.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1915.17 1720.96 L1915.17 1720.96 L1915.45 1720.96 L1915.45 1720.96 L1915.17 1720.96 L1915.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1915.17,1720.96 1915.17,1720.96 1915.45,1720.96 1915.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1915.45 1720.96 L1915.45 1720.96 L1915.73 1720.96 L1915.73 1720.96 L1915.45 1720.96 L1915.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1915.45,1720.96 1915.45,1720.96 1915.73,1720.96 1915.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1915.73 1720.96 L1915.73 1720.96 L1916.01 1720.96 L1916.01 1720.96 L1915.73 1720.96 L1915.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1915.73,1720.96 1915.73,1720.96 1916.01,1720.96 1915.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1916.01 1720.96 L1916.01 1720.96 L1916.3 1720.96 L1916.3 1720.96 L1916.01 1720.96 L1916.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1916.01,1720.96 1916.01,1720.96 1916.3,1720.96 1916.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1916.3 1720.96 L1916.3 1720.96 L1916.58 1720.96 L1916.58 1720.96 L1916.3 1720.96 L1916.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1916.3,1720.96 1916.3,1720.96 1916.58,1720.96 1916.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1916.58 1720.96 L1916.58 1720.96 L1916.86 1720.96 L1916.86 1720.96 L1916.58 1720.96 L1916.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1916.58,1720.96 1916.58,1720.96 1916.86,1720.96 1916.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1916.86 1720.96 L1916.86 1720.96 L1917.14 1720.96 L1917.14 1720.96 L1916.86 1720.96 L1916.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1916.86,1720.96 1916.86,1720.96 1917.14,1720.96 1916.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1917.14 1720.96 L1917.14 1720.96 L1917.42 1720.96 L1917.42 1720.96 L1917.14 1720.96 L1917.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1917.14,1720.96 1917.14,1720.96 1917.42,1720.96 1917.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1917.42 1720.96 L1917.42 1720.96 L1917.7 1720.96 L1917.7 1720.96 L1917.42 1720.96 L1917.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1917.42,1720.96 1917.42,1720.96 1917.7,1720.96 1917.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1917.7 1720.96 L1917.7 1720.96 L1917.99 1720.96 L1917.99 1720.96 L1917.7 1720.96 L1917.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1917.7,1720.96 1917.7,1720.96 1917.99,1720.96 1917.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1917.99 1720.96 L1917.99 1720.96 L1918.27 1720.96 L1918.27 1720.96 L1917.99 1720.96 L1917.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1917.99,1720.96 1917.99,1720.96 1918.27,1720.96 1917.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1918.27 1720.96 L1918.27 1720.96 L1918.55 1720.96 L1918.55 1720.96 L1918.27 1720.96 L1918.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1918.27,1720.96 1918.27,1720.96 1918.55,1720.96 1918.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1918.55 1720.96 L1918.55 1720.96 L1918.83 1720.96 L1918.83 1720.96 L1918.55 1720.96 L1918.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1918.55,1720.96 1918.55,1720.96 1918.83,1720.96 1918.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1918.83 1720.96 L1918.83 1720.96 L1919.11 1720.96 L1919.11 1720.96 L1918.83 1720.96 L1918.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1918.83,1720.96 1918.83,1720.96 1919.11,1720.96 1918.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1919.11 1720.96 L1919.11 1720.96 L1919.39 1720.96 L1919.39 1720.96 L1919.11 1720.96 L1919.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1919.11,1720.96 1919.11,1720.96 1919.39,1720.96 1919.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1919.39 1720.96 L1919.39 1720.96 L1919.68 1720.96 L1919.68 1720.96 L1919.39 1720.96 L1919.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1919.39,1720.96 1919.39,1720.96 1919.68,1720.96 1919.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1919.68 1720.96 L1919.68 1720.96 L1919.96 1720.96 L1919.96 1720.96 L1919.68 1720.96 L1919.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1919.68,1720.96 1919.68,1720.96 1919.96,1720.96 1919.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1919.96 1720.96 L1919.96 1720.96 L1920.24 1720.96 L1920.24 1720.96 L1919.96 1720.96 L1919.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1919.96,1720.96 1919.96,1720.96 1920.24,1720.96 1919.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1920.24 1720.96 L1920.24 1720.96 L1920.52 1720.96 L1920.52 1720.96 L1920.24 1720.96 L1920.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1920.24,1720.96 1920.24,1720.96 1920.52,1720.96 1920.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1920.52 1720.96 L1920.52 1720.96 L1920.8 1720.96 L1920.8 1720.96 L1920.52 1720.96 L1920.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1920.52,1720.96 1920.52,1720.96 1920.8,1720.96 1920.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1920.8 1720.96 L1920.8 1720.96 L1921.08 1720.96 L1921.08 1720.96 L1920.8 1720.96 L1920.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1920.8,1720.96 1920.8,1720.96 1921.08,1720.96 1920.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1921.08 1720.96 L1921.08 1720.96 L1921.37 1720.96 L1921.37 1720.96 L1921.08 1720.96 L1921.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1921.08,1720.96 1921.08,1720.96 1921.37,1720.96 1921.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1921.37 1720.96 L1921.37 1720.96 L1921.65 1720.96 L1921.65 1720.96 L1921.37 1720.96 L1921.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1921.37,1720.96 1921.37,1720.96 1921.65,1720.96 1921.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1921.65 1720.96 L1921.65 1720.96 L1921.93 1720.96 L1921.93 1720.96 L1921.65 1720.96 L1921.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1921.65,1720.96 1921.65,1720.96 1921.93,1720.96 1921.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1921.93 1720.96 L1921.93 1720.96 L1922.21 1720.96 L1922.21 1720.96 L1921.93 1720.96 L1921.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1921.93,1720.96 1921.93,1720.96 1922.21,1720.96 1921.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1922.21 1720.96 L1922.21 1720.96 L1922.49 1720.96 L1922.49 1720.96 L1922.21 1720.96 L1922.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1922.21,1720.96 1922.21,1720.96 1922.49,1720.96 1922.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1922.49 1720.96 L1922.49 1720.96 L1922.78 1720.96 L1922.78 1720.96 L1922.49 1720.96 L1922.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1922.49,1720.96 1922.49,1720.96 1922.78,1720.96 1922.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1922.78 1720.96 L1922.78 1720.96 L1923.06 1720.96 L1923.06 1720.96 L1922.78 1720.96 L1922.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1922.78,1720.96 1922.78,1720.96 1923.06,1720.96 1922.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1923.06 1720.96 L1923.06 1720.96 L1923.34 1720.96 L1923.34 1720.96 L1923.06 1720.96 L1923.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1923.06,1720.96 1923.06,1720.96 1923.34,1720.96 1923.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1923.34 1720.96 L1923.34 1720.96 L1923.62 1720.96 L1923.62 1720.96 L1923.34 1720.96 L1923.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1923.34,1720.96 1923.34,1720.96 1923.62,1720.96 1923.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1923.62 1720.96 L1923.62 1720.96 L1923.9 1720.96 L1923.9 1720.96 L1923.62 1720.96 L1923.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1923.62,1720.96 1923.62,1720.96 1923.9,1720.96 1923.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1923.9 1720.96 L1923.9 1720.96 L1924.18 1720.96 L1924.18 1720.96 L1923.9 1720.96 L1923.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1923.9,1720.96 1923.9,1720.96 1924.18,1720.96 1923.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1924.18 1720.96 L1924.18 1720.96 L1924.47 1720.96 L1924.47 1720.96 L1924.18 1720.96 L1924.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1924.18,1720.96 1924.18,1720.96 1924.47,1720.96 1924.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1924.47 1720.96 L1924.47 1720.96 L1924.75 1720.96 L1924.75 1720.96 L1924.47 1720.96 L1924.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1924.47,1720.96 1924.47,1720.96 1924.75,1720.96 1924.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1924.75 1720.96 L1924.75 1720.96 L1925.03 1720.96 L1925.03 1720.96 L1924.75 1720.96 L1924.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1924.75,1720.96 1924.75,1720.96 1925.03,1720.96 1924.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1925.03 1720.96 L1925.03 1720.96 L1925.31 1720.96 L1925.31 1720.96 L1925.03 1720.96 L1925.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1925.03,1720.96 1925.03,1720.96 1925.31,1720.96 1925.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1925.31 1720.96 L1925.31 1720.96 L1925.59 1720.96 L1925.59 1720.96 L1925.31 1720.96 L1925.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1925.31,1720.96 1925.31,1720.96 1925.59,1720.96 1925.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1925.59 1720.96 L1925.59 1720.96 L1925.87 1720.96 L1925.87 1720.96 L1925.59 1720.96 L1925.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1925.59,1720.96 1925.59,1720.96 1925.87,1720.96 1925.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1925.87 1720.96 L1925.87 1720.96 L1926.16 1720.96 L1926.16 1720.96 L1925.87 1720.96 L1925.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1925.87,1720.96 1925.87,1720.96 1926.16,1720.96 1925.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1926.16 1720.96 L1926.16 1720.96 L1926.44 1720.96 L1926.44 1720.96 L1926.16 1720.96 L1926.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1926.16,1720.96 1926.16,1720.96 1926.44,1720.96 1926.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1926.44 1720.96 L1926.44 1720.96 L1926.72 1720.96 L1926.72 1720.96 L1926.44 1720.96 L1926.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1926.44,1720.96 1926.44,1720.96 1926.72,1720.96 1926.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1926.72 1720.96 L1926.72 1720.96 L1927 1720.96 L1927 1720.96 L1926.72 1720.96 L1926.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1926.72,1720.96 1926.72,1720.96 1927,1720.96 1926.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1927 1720.96 L1927 1720.96 L1927.28 1720.96 L1927.28 1720.96 L1927 1720.96 L1927 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1927,1720.96 1927,1720.96 1927.28,1720.96 1927,1720.96 "/>
<path clip-path="url(#clip322)" d="M1927.28 1720.96 L1927.28 1720.96 L1927.56 1720.96 L1927.56 1720.96 L1927.28 1720.96 L1927.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1927.28,1720.96 1927.28,1720.96 1927.56,1720.96 1927.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1927.56 1720.96 L1927.56 1720.96 L1927.85 1720.96 L1927.85 1720.96 L1927.56 1720.96 L1927.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1927.56,1720.96 1927.56,1720.96 1927.85,1720.96 1927.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1927.85 1720.96 L1927.85 1720.96 L1928.13 1720.96 L1928.13 1720.96 L1927.85 1720.96 L1927.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1927.85,1720.96 1927.85,1720.96 1928.13,1720.96 1927.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1928.13 1720.96 L1928.13 1720.96 L1928.41 1720.96 L1928.41 1720.96 L1928.13 1720.96 L1928.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1928.13,1720.96 1928.13,1720.96 1928.41,1720.96 1928.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1928.41 1720.96 L1928.41 1720.96 L1928.69 1720.96 L1928.69 1720.96 L1928.41 1720.96 L1928.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1928.41,1720.96 1928.41,1720.96 1928.69,1720.96 1928.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1928.69 1720.96 L1928.69 1720.96 L1928.97 1720.96 L1928.97 1720.96 L1928.69 1720.96 L1928.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1928.69,1720.96 1928.69,1720.96 1928.97,1720.96 1928.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1928.97 1720.96 L1928.97 1720.96 L1929.25 1720.96 L1929.25 1720.96 L1928.97 1720.96 L1928.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1928.97,1720.96 1928.97,1720.96 1929.25,1720.96 1928.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1929.25 1720.96 L1929.25 1720.96 L1929.54 1720.96 L1929.54 1720.96 L1929.25 1720.96 L1929.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1929.25,1720.96 1929.25,1720.96 1929.54,1720.96 1929.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1929.54 1720.96 L1929.54 1720.96 L1929.82 1720.96 L1929.82 1720.96 L1929.54 1720.96 L1929.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1929.54,1720.96 1929.54,1720.96 1929.82,1720.96 1929.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1929.82 1720.96 L1929.82 1720.96 L1930.1 1720.96 L1930.1 1720.96 L1929.82 1720.96 L1929.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1929.82,1720.96 1929.82,1720.96 1930.1,1720.96 1929.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1930.1 1720.96 L1930.1 1720.96 L1930.38 1720.96 L1930.38 1720.96 L1930.1 1720.96 L1930.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1930.1,1720.96 1930.1,1720.96 1930.38,1720.96 1930.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1930.38 1720.96 L1930.38 1720.96 L1930.66 1720.96 L1930.66 1720.96 L1930.38 1720.96 L1930.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1930.38,1720.96 1930.38,1720.96 1930.66,1720.96 1930.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1930.66 1720.96 L1930.66 1720.96 L1930.95 1720.96 L1930.95 1720.96 L1930.66 1720.96 L1930.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1930.66,1720.96 1930.66,1720.96 1930.95,1720.96 1930.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1930.95 1720.96 L1930.95 1720.96 L1931.23 1720.96 L1931.23 1720.96 L1930.95 1720.96 L1930.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1930.95,1720.96 1930.95,1720.96 1931.23,1720.96 1930.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1931.23 1720.96 L1931.23 1720.96 L1931.51 1720.96 L1931.51 1720.96 L1931.23 1720.96 L1931.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1931.23,1720.96 1931.23,1720.96 1931.51,1720.96 1931.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1931.51 1720.96 L1931.51 1720.96 L1931.79 1720.96 L1931.79 1720.96 L1931.51 1720.96 L1931.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1931.51,1720.96 1931.51,1720.96 1931.79,1720.96 1931.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1931.79 1720.96 L1931.79 1720.96 L1932.07 1720.96 L1932.07 1720.96 L1931.79 1720.96 L1931.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1931.79,1720.96 1931.79,1720.96 1932.07,1720.96 1931.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1932.07 1720.96 L1932.07 1720.96 L1932.35 1720.96 L1932.35 1720.96 L1932.07 1720.96 L1932.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1932.07,1720.96 1932.07,1720.96 1932.35,1720.96 1932.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1932.35 1720.96 L1932.35 1720.96 L1932.64 1720.96 L1932.64 1720.96 L1932.35 1720.96 L1932.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1932.35,1720.96 1932.35,1720.96 1932.64,1720.96 1932.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1932.64 1720.96 L1932.64 1720.96 L1932.92 1720.96 L1932.92 1720.96 L1932.64 1720.96 L1932.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1932.64,1720.96 1932.64,1720.96 1932.92,1720.96 1932.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1932.92 1720.96 L1932.92 1720.96 L1933.2 1720.96 L1933.2 1720.96 L1932.92 1720.96 L1932.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1932.92,1720.96 1932.92,1720.96 1933.2,1720.96 1932.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1933.2 1720.96 L1933.2 1720.96 L1933.48 1720.96 L1933.48 1720.96 L1933.2 1720.96 L1933.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1933.2,1720.96 1933.2,1720.96 1933.48,1720.96 1933.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1933.48 1720.96 L1933.48 1720.96 L1933.76 1720.96 L1933.76 1720.96 L1933.48 1720.96 L1933.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1933.48,1720.96 1933.48,1720.96 1933.76,1720.96 1933.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1933.76 1720.96 L1933.76 1720.96 L1934.04 1720.96 L1934.04 1720.96 L1933.76 1720.96 L1933.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1933.76,1720.96 1933.76,1720.96 1934.04,1720.96 1933.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1934.04 1720.96 L1934.04 1720.96 L1934.33 1720.96 L1934.33 1720.96 L1934.04 1720.96 L1934.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1934.04,1720.96 1934.04,1720.96 1934.33,1720.96 1934.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1934.33 1720.96 L1934.33 1720.96 L1934.61 1720.96 L1934.61 1720.96 L1934.33 1720.96 L1934.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1934.33,1720.96 1934.33,1720.96 1934.61,1720.96 1934.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1934.61 1720.96 L1934.61 1720.96 L1934.89 1720.96 L1934.89 1720.96 L1934.61 1720.96 L1934.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1934.61,1720.96 1934.61,1720.96 1934.89,1720.96 1934.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1934.89 1720.96 L1934.89 1720.96 L1935.17 1720.96 L1935.17 1720.96 L1934.89 1720.96 L1934.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1934.89,1720.96 1934.89,1720.96 1935.17,1720.96 1934.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1935.17 1720.96 L1935.17 1720.96 L1935.45 1720.96 L1935.45 1720.96 L1935.17 1720.96 L1935.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1935.17,1720.96 1935.17,1720.96 1935.45,1720.96 1935.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1935.45 1720.96 L1935.45 1720.96 L1935.73 1720.96 L1935.73 1720.96 L1935.45 1720.96 L1935.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1935.45,1720.96 1935.45,1720.96 1935.73,1720.96 1935.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1935.73 1720.96 L1935.73 1720.96 L1936.02 1720.96 L1936.02 1720.96 L1935.73 1720.96 L1935.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1935.73,1720.96 1935.73,1720.96 1936.02,1720.96 1935.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1936.02 1720.96 L1936.02 1720.96 L1936.3 1720.96 L1936.3 1720.96 L1936.02 1720.96 L1936.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1936.02,1720.96 1936.02,1720.96 1936.3,1720.96 1936.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1936.3 1720.96 L1936.3 1720.96 L1936.58 1720.96 L1936.58 1720.96 L1936.3 1720.96 L1936.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1936.3,1720.96 1936.3,1720.96 1936.58,1720.96 1936.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1936.58 1720.96 L1936.58 1720.96 L1936.86 1720.96 L1936.86 1720.96 L1936.58 1720.96 L1936.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1936.58,1720.96 1936.58,1720.96 1936.86,1720.96 1936.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1936.86 1720.96 L1936.86 1720.96 L1937.14 1720.96 L1937.14 1720.96 L1936.86 1720.96 L1936.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1936.86,1720.96 1936.86,1720.96 1937.14,1720.96 1936.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1937.14 1720.96 L1937.14 1720.96 L1937.42 1720.96 L1937.42 1720.96 L1937.14 1720.96 L1937.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1937.14,1720.96 1937.14,1720.96 1937.42,1720.96 1937.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1937.42 1720.96 L1937.42 1720.96 L1937.71 1720.96 L1937.71 1720.96 L1937.42 1720.96 L1937.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1937.42,1720.96 1937.42,1720.96 1937.71,1720.96 1937.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1937.71 1720.96 L1937.71 1720.96 L1937.99 1720.96 L1937.99 1720.96 L1937.71 1720.96 L1937.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1937.71,1720.96 1937.71,1720.96 1937.99,1720.96 1937.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1937.99 1720.96 L1937.99 1720.96 L1938.27 1720.96 L1938.27 1720.96 L1937.99 1720.96 L1937.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1937.99,1720.96 1937.99,1720.96 1938.27,1720.96 1937.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1938.27 1720.96 L1938.27 1720.96 L1938.55 1720.96 L1938.55 1720.96 L1938.27 1720.96 L1938.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1938.27,1720.96 1938.27,1720.96 1938.55,1720.96 1938.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1938.55 1720.96 L1938.55 1720.96 L1938.83 1720.96 L1938.83 1720.96 L1938.55 1720.96 L1938.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1938.55,1720.96 1938.55,1720.96 1938.83,1720.96 1938.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1938.83 1720.96 L1938.83 1720.96 L1939.12 1720.96 L1939.12 1720.96 L1938.83 1720.96 L1938.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1938.83,1720.96 1938.83,1720.96 1939.12,1720.96 1938.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1939.12 1720.96 L1939.12 1720.96 L1939.4 1720.96 L1939.4 1720.96 L1939.12 1720.96 L1939.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1939.12,1720.96 1939.12,1720.96 1939.4,1720.96 1939.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1939.4 1720.96 L1939.4 1720.96 L1939.68 1720.96 L1939.68 1720.96 L1939.4 1720.96 L1939.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1939.4,1720.96 1939.4,1720.96 1939.68,1720.96 1939.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1939.68 1720.96 L1939.68 1720.96 L1939.96 1720.96 L1939.96 1720.96 L1939.68 1720.96 L1939.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1939.68,1720.96 1939.68,1720.96 1939.96,1720.96 1939.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1939.96 1720.96 L1939.96 1720.96 L1940.24 1720.96 L1940.24 1720.96 L1939.96 1720.96 L1939.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1939.96,1720.96 1939.96,1720.96 1940.24,1720.96 1939.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1940.24 1720.96 L1940.24 1720.96 L1940.52 1720.96 L1940.52 1720.96 L1940.24 1720.96 L1940.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1940.24,1720.96 1940.24,1720.96 1940.52,1720.96 1940.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1940.52 1720.96 L1940.52 1720.96 L1940.81 1720.96 L1940.81 1720.96 L1940.52 1720.96 L1940.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1940.52,1720.96 1940.52,1720.96 1940.81,1720.96 1940.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1940.81 1720.96 L1940.81 1720.96 L1941.09 1720.96 L1941.09 1720.96 L1940.81 1720.96 L1940.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1940.81,1720.96 1940.81,1720.96 1941.09,1720.96 1940.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1941.09 1720.96 L1941.09 1720.96 L1941.37 1720.96 L1941.37 1720.96 L1941.09 1720.96 L1941.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1941.09,1720.96 1941.09,1720.96 1941.37,1720.96 1941.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1941.37 1720.96 L1941.37 1720.96 L1941.65 1720.96 L1941.65 1720.96 L1941.37 1720.96 L1941.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1941.37,1720.96 1941.37,1720.96 1941.65,1720.96 1941.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1941.65 1720.96 L1941.65 1720.96 L1941.93 1720.96 L1941.93 1720.96 L1941.65 1720.96 L1941.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1941.65,1720.96 1941.65,1720.96 1941.93,1720.96 1941.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1941.93 1720.96 L1941.93 1720.96 L1942.21 1720.96 L1942.21 1720.96 L1941.93 1720.96 L1941.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1941.93,1720.96 1941.93,1720.96 1942.21,1720.96 1941.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1942.21 1720.96 L1942.21 1720.96 L1942.5 1720.96 L1942.5 1720.96 L1942.21 1720.96 L1942.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1942.21,1720.96 1942.21,1720.96 1942.5,1720.96 1942.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1942.5 1720.96 L1942.5 1720.96 L1942.78 1720.96 L1942.78 1720.96 L1942.5 1720.96 L1942.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1942.5,1720.96 1942.5,1720.96 1942.78,1720.96 1942.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1942.78 1720.96 L1942.78 1720.96 L1943.06 1720.96 L1943.06 1720.96 L1942.78 1720.96 L1942.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1942.78,1720.96 1942.78,1720.96 1943.06,1720.96 1942.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1943.06 1720.96 L1943.06 1720.96 L1943.34 1720.96 L1943.34 1720.96 L1943.06 1720.96 L1943.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1943.06,1720.96 1943.06,1720.96 1943.34,1720.96 1943.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1943.34 1720.96 L1943.34 1720.96 L1943.62 1720.96 L1943.62 1720.96 L1943.34 1720.96 L1943.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1943.34,1720.96 1943.34,1720.96 1943.62,1720.96 1943.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1943.62 1720.96 L1943.62 1720.96 L1943.9 1720.96 L1943.9 1720.96 L1943.62 1720.96 L1943.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1943.62,1720.96 1943.62,1720.96 1943.9,1720.96 1943.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1943.9 1720.96 L1943.9 1720.96 L1944.19 1720.96 L1944.19 1720.96 L1943.9 1720.96 L1943.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1943.9,1720.96 1943.9,1720.96 1944.19,1720.96 1943.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1944.19 1720.96 L1944.19 1720.96 L1944.47 1720.96 L1944.47 1720.96 L1944.19 1720.96 L1944.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1944.19,1720.96 1944.19,1720.96 1944.47,1720.96 1944.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1944.47 1720.96 L1944.47 1720.96 L1944.75 1720.96 L1944.75 1720.96 L1944.47 1720.96 L1944.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1944.47,1720.96 1944.47,1720.96 1944.75,1720.96 1944.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1944.75 1720.96 L1944.75 1720.96 L1945.03 1720.96 L1945.03 1720.96 L1944.75 1720.96 L1944.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1944.75,1720.96 1944.75,1720.96 1945.03,1720.96 1944.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1945.03 1720.96 L1945.03 1720.96 L1945.31 1720.96 L1945.31 1720.96 L1945.03 1720.96 L1945.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1945.03,1720.96 1945.03,1720.96 1945.31,1720.96 1945.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1945.31 1720.96 L1945.31 1720.96 L1945.59 1720.96 L1945.59 1720.96 L1945.31 1720.96 L1945.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1945.31,1720.96 1945.31,1720.96 1945.59,1720.96 1945.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1945.59 1720.96 L1945.59 1720.96 L1945.88 1720.96 L1945.88 1720.96 L1945.59 1720.96 L1945.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1945.59,1720.96 1945.59,1720.96 1945.88,1720.96 1945.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1945.88 1720.96 L1945.88 1720.96 L1946.16 1720.96 L1946.16 1720.96 L1945.88 1720.96 L1945.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1945.88,1720.96 1945.88,1720.96 1946.16,1720.96 1945.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1946.16 1720.96 L1946.16 1720.96 L1946.44 1720.96 L1946.44 1720.96 L1946.16 1720.96 L1946.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1946.16,1720.96 1946.16,1720.96 1946.44,1720.96 1946.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1946.44 1720.96 L1946.44 1720.96 L1946.72 1720.96 L1946.72 1720.96 L1946.44 1720.96 L1946.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1946.44,1720.96 1946.44,1720.96 1946.72,1720.96 1946.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1946.72 1720.96 L1946.72 1720.96 L1947 1720.96 L1947 1720.96 L1946.72 1720.96 L1946.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1946.72,1720.96 1946.72,1720.96 1947,1720.96 1946.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1947 1720.96 L1947 1720.96 L1947.29 1720.96 L1947.29 1720.96 L1947 1720.96 L1947 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1947,1720.96 1947,1720.96 1947.29,1720.96 1947,1720.96 "/>
<path clip-path="url(#clip322)" d="M1947.29 1720.96 L1947.29 1720.96 L1947.57 1720.96 L1947.57 1720.96 L1947.29 1720.96 L1947.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1947.29,1720.96 1947.29,1720.96 1947.57,1720.96 1947.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1947.57 1720.96 L1947.57 1720.96 L1947.85 1720.96 L1947.85 1720.96 L1947.57 1720.96 L1947.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1947.57,1720.96 1947.57,1720.96 1947.85,1720.96 1947.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1947.85 1720.96 L1947.85 1720.96 L1948.13 1720.96 L1948.13 1720.96 L1947.85 1720.96 L1947.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1947.85,1720.96 1947.85,1720.96 1948.13,1720.96 1947.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1948.13 1720.96 L1948.13 1720.96 L1948.41 1720.96 L1948.41 1720.96 L1948.13 1720.96 L1948.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1948.13,1720.96 1948.13,1720.96 1948.41,1720.96 1948.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1948.41 1720.96 L1948.41 1720.96 L1948.69 1720.96 L1948.69 1720.96 L1948.41 1720.96 L1948.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1948.41,1720.96 1948.41,1720.96 1948.69,1720.96 1948.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1948.69 1720.96 L1948.69 1720.96 L1948.98 1720.96 L1948.98 1720.96 L1948.69 1720.96 L1948.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1948.69,1720.96 1948.69,1720.96 1948.98,1720.96 1948.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1948.98 1720.96 L1948.98 1720.96 L1949.26 1720.96 L1949.26 1720.96 L1948.98 1720.96 L1948.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1948.98,1720.96 1948.98,1720.96 1949.26,1720.96 1948.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1949.26 1720.96 L1949.26 1720.96 L1949.54 1720.96 L1949.54 1720.96 L1949.26 1720.96 L1949.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1949.26,1720.96 1949.26,1720.96 1949.54,1720.96 1949.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1949.54 1720.96 L1949.54 1720.96 L1949.82 1720.96 L1949.82 1720.96 L1949.54 1720.96 L1949.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1949.54,1720.96 1949.54,1720.96 1949.82,1720.96 1949.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1949.82 1720.96 L1949.82 1720.96 L1950.1 1720.96 L1950.1 1720.96 L1949.82 1720.96 L1949.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1949.82,1720.96 1949.82,1720.96 1950.1,1720.96 1949.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1950.1 1720.96 L1950.1 1720.96 L1950.38 1720.96 L1950.38 1720.96 L1950.1 1720.96 L1950.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1950.1,1720.96 1950.1,1720.96 1950.38,1720.96 1950.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1950.38 1720.96 L1950.38 1720.96 L1950.67 1720.96 L1950.67 1720.96 L1950.38 1720.96 L1950.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1950.38,1720.96 1950.38,1720.96 1950.67,1720.96 1950.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M1950.67 1720.96 L1950.67 1720.96 L1950.95 1720.96 L1950.95 1720.96 L1950.67 1720.96 L1950.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1950.67,1720.96 1950.67,1720.96 1950.95,1720.96 1950.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1950.95 1720.96 L1950.95 1720.96 L1951.23 1720.96 L1951.23 1720.96 L1950.95 1720.96 L1950.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1950.95,1720.96 1950.95,1720.96 1951.23,1720.96 1950.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1951.23 1720.96 L1951.23 1720.96 L1951.51 1720.96 L1951.51 1720.96 L1951.23 1720.96 L1951.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1951.23,1720.96 1951.23,1720.96 1951.51,1720.96 1951.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1951.51 1720.96 L1951.51 1720.96 L1951.79 1720.96 L1951.79 1720.96 L1951.51 1720.96 L1951.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1951.51,1720.96 1951.51,1720.96 1951.79,1720.96 1951.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1951.79 1720.96 L1951.79 1720.96 L1952.07 1720.96 L1952.07 1720.96 L1951.79 1720.96 L1951.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1951.79,1720.96 1951.79,1720.96 1952.07,1720.96 1951.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M1952.07 1720.96 L1952.07 1720.96 L1952.36 1720.96 L1952.36 1720.96 L1952.07 1720.96 L1952.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1952.07,1720.96 1952.07,1720.96 1952.36,1720.96 1952.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M1952.36 1720.96 L1952.36 1720.96 L1952.64 1720.96 L1952.64 1720.96 L1952.36 1720.96 L1952.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1952.36,1720.96 1952.36,1720.96 1952.64,1720.96 1952.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1952.64 1720.96 L1952.64 1720.96 L1952.92 1720.96 L1952.92 1720.96 L1952.64 1720.96 L1952.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1952.64,1720.96 1952.64,1720.96 1952.92,1720.96 1952.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1952.92 1720.96 L1952.92 1720.96 L1953.2 1720.96 L1953.2 1720.96 L1952.92 1720.96 L1952.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1952.92,1720.96 1952.92,1720.96 1953.2,1720.96 1952.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1953.2 1720.96 L1953.2 1720.96 L1953.48 1720.96 L1953.48 1720.96 L1953.2 1720.96 L1953.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1953.2,1720.96 1953.2,1720.96 1953.48,1720.96 1953.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1953.48 1720.96 L1953.48 1720.96 L1953.76 1720.96 L1953.76 1720.96 L1953.48 1720.96 L1953.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1953.48,1720.96 1953.48,1720.96 1953.76,1720.96 1953.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M1953.76 1720.96 L1953.76 1720.96 L1954.05 1720.96 L1954.05 1720.96 L1953.76 1720.96 L1953.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1953.76,1720.96 1953.76,1720.96 1954.05,1720.96 1953.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M1954.05 1720.96 L1954.05 1720.96 L1954.33 1720.96 L1954.33 1720.96 L1954.05 1720.96 L1954.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1954.05,1720.96 1954.05,1720.96 1954.33,1720.96 1954.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1954.33 1720.96 L1954.33 1720.96 L1954.61 1720.96 L1954.61 1720.96 L1954.33 1720.96 L1954.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1954.33,1720.96 1954.33,1720.96 1954.61,1720.96 1954.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1954.61 1720.96 L1954.61 1720.96 L1954.89 1720.96 L1954.89 1720.96 L1954.61 1720.96 L1954.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1954.61,1720.96 1954.61,1720.96 1954.89,1720.96 1954.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1954.89 1720.96 L1954.89 1720.96 L1955.17 1720.96 L1955.17 1720.96 L1954.89 1720.96 L1954.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1954.89,1720.96 1954.89,1720.96 1955.17,1720.96 1954.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1955.17 1720.96 L1955.17 1720.96 L1955.46 1720.96 L1955.46 1720.96 L1955.17 1720.96 L1955.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1955.17,1720.96 1955.17,1720.96 1955.46,1720.96 1955.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M1955.46 1720.96 L1955.46 1720.96 L1955.74 1720.96 L1955.74 1720.96 L1955.46 1720.96 L1955.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1955.46,1720.96 1955.46,1720.96 1955.74,1720.96 1955.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1955.74 1720.96 L1955.74 1720.96 L1956.02 1720.96 L1956.02 1720.96 L1955.74 1720.96 L1955.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1955.74,1720.96 1955.74,1720.96 1956.02,1720.96 1955.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1956.02 1720.96 L1956.02 1720.96 L1956.3 1720.96 L1956.3 1720.96 L1956.02 1720.96 L1956.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1956.02,1720.96 1956.02,1720.96 1956.3,1720.96 1956.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1956.3 1720.96 L1956.3 1720.96 L1956.58 1720.96 L1956.58 1720.96 L1956.3 1720.96 L1956.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1956.3,1720.96 1956.3,1720.96 1956.58,1720.96 1956.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1956.58 1720.96 L1956.58 1720.96 L1956.86 1720.96 L1956.86 1720.96 L1956.58 1720.96 L1956.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1956.58,1720.96 1956.58,1720.96 1956.86,1720.96 1956.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1956.86 1720.96 L1956.86 1720.96 L1957.15 1720.96 L1957.15 1720.96 L1956.86 1720.96 L1956.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1956.86,1720.96 1956.86,1720.96 1957.15,1720.96 1956.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M1957.15 1720.96 L1957.15 1720.96 L1957.43 1720.96 L1957.43 1720.96 L1957.15 1720.96 L1957.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1957.15,1720.96 1957.15,1720.96 1957.43,1720.96 1957.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1957.43 1720.96 L1957.43 1720.96 L1957.71 1720.96 L1957.71 1720.96 L1957.43 1720.96 L1957.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1957.43,1720.96 1957.43,1720.96 1957.71,1720.96 1957.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1957.71 1720.96 L1957.71 1720.96 L1957.99 1720.96 L1957.99 1720.96 L1957.71 1720.96 L1957.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1957.71,1720.96 1957.71,1720.96 1957.99,1720.96 1957.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1957.99 1720.96 L1957.99 1720.96 L1958.27 1720.96 L1958.27 1720.96 L1957.99 1720.96 L1957.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1957.99,1720.96 1957.99,1720.96 1958.27,1720.96 1957.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1958.27 1720.96 L1958.27 1720.96 L1958.55 1720.96 L1958.55 1720.96 L1958.27 1720.96 L1958.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1958.27,1720.96 1958.27,1720.96 1958.55,1720.96 1958.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1958.55 1720.96 L1958.55 1720.96 L1958.84 1720.96 L1958.84 1720.96 L1958.55 1720.96 L1958.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1958.55,1720.96 1958.55,1720.96 1958.84,1720.96 1958.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M1958.84 1720.96 L1958.84 1720.96 L1959.12 1720.96 L1959.12 1720.96 L1958.84 1720.96 L1958.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1958.84,1720.96 1958.84,1720.96 1959.12,1720.96 1958.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1959.12 1720.96 L1959.12 1720.96 L1959.4 1720.96 L1959.4 1720.96 L1959.12 1720.96 L1959.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1959.12,1720.96 1959.12,1720.96 1959.4,1720.96 1959.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1959.4 1720.96 L1959.4 1720.96 L1959.68 1720.96 L1959.68 1720.96 L1959.4 1720.96 L1959.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1959.4,1720.96 1959.4,1720.96 1959.68,1720.96 1959.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1959.68 1720.96 L1959.68 1720.96 L1959.96 1720.96 L1959.96 1720.96 L1959.68 1720.96 L1959.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1959.68,1720.96 1959.68,1720.96 1959.96,1720.96 1959.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1959.96 1720.96 L1959.96 1720.96 L1960.24 1720.96 L1960.24 1720.96 L1959.96 1720.96 L1959.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1959.96,1720.96 1959.96,1720.96 1960.24,1720.96 1959.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M1960.24 1720.96 L1960.24 1720.96 L1960.53 1720.96 L1960.53 1720.96 L1960.24 1720.96 L1960.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1960.24,1720.96 1960.24,1720.96 1960.53,1720.96 1960.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M1960.53 1720.96 L1960.53 1720.96 L1960.81 1720.96 L1960.81 1720.96 L1960.53 1720.96 L1960.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1960.53,1720.96 1960.53,1720.96 1960.81,1720.96 1960.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1960.81 1720.96 L1960.81 1720.96 L1961.09 1720.96 L1961.09 1720.96 L1960.81 1720.96 L1960.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1960.81,1720.96 1960.81,1720.96 1961.09,1720.96 1960.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1961.09 1720.96 L1961.09 1720.96 L1961.37 1720.96 L1961.37 1720.96 L1961.09 1720.96 L1961.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1961.09,1720.96 1961.09,1720.96 1961.37,1720.96 1961.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1961.37 1720.96 L1961.37 1720.96 L1961.65 1720.96 L1961.65 1720.96 L1961.37 1720.96 L1961.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1961.37,1720.96 1961.37,1720.96 1961.65,1720.96 1961.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1961.65 1720.96 L1961.65 1720.96 L1961.93 1720.96 L1961.93 1720.96 L1961.65 1720.96 L1961.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1961.65,1720.96 1961.65,1720.96 1961.93,1720.96 1961.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M1961.93 1720.96 L1961.93 1720.96 L1962.22 1720.96 L1962.22 1720.96 L1961.93 1720.96 L1961.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1961.93,1720.96 1961.93,1720.96 1962.22,1720.96 1961.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M1962.22 1720.96 L1962.22 1720.96 L1962.5 1720.96 L1962.5 1720.96 L1962.22 1720.96 L1962.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1962.22,1720.96 1962.22,1720.96 1962.5,1720.96 1962.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1962.5 1720.96 L1962.5 1720.96 L1962.78 1720.96 L1962.78 1720.96 L1962.5 1720.96 L1962.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1962.5,1720.96 1962.5,1720.96 1962.78,1720.96 1962.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1962.78 1720.96 L1962.78 1720.96 L1963.06 1720.96 L1963.06 1720.96 L1962.78 1720.96 L1962.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1962.78,1720.96 1962.78,1720.96 1963.06,1720.96 1962.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1963.06 1720.96 L1963.06 1720.96 L1963.34 1720.96 L1963.34 1720.96 L1963.06 1720.96 L1963.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1963.06,1720.96 1963.06,1720.96 1963.34,1720.96 1963.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1963.34 1720.96 L1963.34 1720.96 L1963.63 1720.96 L1963.63 1720.96 L1963.34 1720.96 L1963.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1963.34,1720.96 1963.34,1720.96 1963.63,1720.96 1963.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M1963.63 1720.96 L1963.63 1720.96 L1963.91 1720.96 L1963.91 1720.96 L1963.63 1720.96 L1963.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1963.63,1720.96 1963.63,1720.96 1963.91,1720.96 1963.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1963.91 1720.96 L1963.91 1720.96 L1964.19 1720.96 L1964.19 1720.96 L1963.91 1720.96 L1963.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1963.91,1720.96 1963.91,1720.96 1964.19,1720.96 1963.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1964.19 1720.96 L1964.19 1720.96 L1964.47 1720.96 L1964.47 1720.96 L1964.19 1720.96 L1964.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1964.19,1720.96 1964.19,1720.96 1964.47,1720.96 1964.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1964.47 1720.96 L1964.47 1720.96 L1964.75 1720.96 L1964.75 1720.96 L1964.47 1720.96 L1964.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1964.47,1720.96 1964.47,1720.96 1964.75,1720.96 1964.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1964.75 1720.96 L1964.75 1720.96 L1965.03 1720.96 L1965.03 1720.96 L1964.75 1720.96 L1964.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1964.75,1720.96 1964.75,1720.96 1965.03,1720.96 1964.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1965.03 1720.96 L1965.03 1720.96 L1965.32 1720.96 L1965.32 1720.96 L1965.03 1720.96 L1965.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1965.03,1720.96 1965.03,1720.96 1965.32,1720.96 1965.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M1965.32 1720.96 L1965.32 1720.96 L1965.6 1720.96 L1965.6 1720.96 L1965.32 1720.96 L1965.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1965.32,1720.96 1965.32,1720.96 1965.6,1720.96 1965.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1965.6 1720.96 L1965.6 1720.96 L1965.88 1720.96 L1965.88 1720.96 L1965.6 1720.96 L1965.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1965.6,1720.96 1965.6,1720.96 1965.88,1720.96 1965.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1965.88 1720.96 L1965.88 1720.96 L1966.16 1720.96 L1966.16 1720.96 L1965.88 1720.96 L1965.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1965.88,1720.96 1965.88,1720.96 1966.16,1720.96 1965.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1966.16 1720.96 L1966.16 1720.96 L1966.44 1720.96 L1966.44 1720.96 L1966.16 1720.96 L1966.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1966.16,1720.96 1966.16,1720.96 1966.44,1720.96 1966.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1966.44 1720.96 L1966.44 1720.96 L1966.72 1720.96 L1966.72 1720.96 L1966.44 1720.96 L1966.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1966.44,1720.96 1966.44,1720.96 1966.72,1720.96 1966.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M1966.72 1720.96 L1966.72 1720.96 L1967.01 1720.96 L1967.01 1720.96 L1966.72 1720.96 L1966.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1966.72,1720.96 1966.72,1720.96 1967.01,1720.96 1966.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M1967.01 1720.96 L1967.01 1720.96 L1967.29 1720.96 L1967.29 1720.96 L1967.01 1720.96 L1967.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1967.01,1720.96 1967.01,1720.96 1967.29,1720.96 1967.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1967.29 1720.96 L1967.29 1720.96 L1967.57 1720.96 L1967.57 1720.96 L1967.29 1720.96 L1967.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1967.29,1720.96 1967.29,1720.96 1967.57,1720.96 1967.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1967.57 1720.96 L1967.57 1720.96 L1967.85 1720.96 L1967.85 1720.96 L1967.57 1720.96 L1967.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1967.57,1720.96 1967.57,1720.96 1967.85,1720.96 1967.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1967.85 1720.96 L1967.85 1720.96 L1968.13 1720.96 L1968.13 1720.96 L1967.85 1720.96 L1967.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1967.85,1720.96 1967.85,1720.96 1968.13,1720.96 1967.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1968.13 1720.96 L1968.13 1720.96 L1968.41 1720.96 L1968.41 1720.96 L1968.13 1720.96 L1968.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1968.13,1720.96 1968.13,1720.96 1968.41,1720.96 1968.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M1968.41 1720.96 L1968.41 1720.96 L1968.7 1720.96 L1968.7 1720.96 L1968.41 1720.96 L1968.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1968.41,1720.96 1968.41,1720.96 1968.7,1720.96 1968.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M1968.7 1720.96 L1968.7 1720.96 L1968.98 1720.96 L1968.98 1720.96 L1968.7 1720.96 L1968.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1968.7,1720.96 1968.7,1720.96 1968.98,1720.96 1968.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1968.98 1720.96 L1968.98 1720.96 L1969.26 1720.96 L1969.26 1720.96 L1968.98 1720.96 L1968.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1968.98,1720.96 1968.98,1720.96 1969.26,1720.96 1968.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1969.26 1720.96 L1969.26 1720.96 L1969.54 1720.96 L1969.54 1720.96 L1969.26 1720.96 L1969.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1969.26,1720.96 1969.26,1720.96 1969.54,1720.96 1969.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1969.54 1720.96 L1969.54 1720.96 L1969.82 1720.96 L1969.82 1720.96 L1969.54 1720.96 L1969.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1969.54,1720.96 1969.54,1720.96 1969.82,1720.96 1969.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1969.82 1720.96 L1969.82 1720.96 L1970.1 1720.96 L1970.1 1720.96 L1969.82 1720.96 L1969.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1969.82,1720.96 1969.82,1720.96 1970.1,1720.96 1969.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M1970.1 1720.96 L1970.1 1720.96 L1970.39 1720.96 L1970.39 1720.96 L1970.1 1720.96 L1970.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1970.1,1720.96 1970.1,1720.96 1970.39,1720.96 1970.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M1970.39 1720.96 L1970.39 1720.96 L1970.67 1720.96 L1970.67 1720.96 L1970.39 1720.96 L1970.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1970.39,1720.96 1970.39,1720.96 1970.67,1720.96 1970.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1970.67 1720.96 L1970.67 1720.96 L1970.95 1720.96 L1970.95 1720.96 L1970.67 1720.96 L1970.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1970.67,1720.96 1970.67,1720.96 1970.95,1720.96 1970.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1970.95 1720.96 L1970.95 1720.96 L1971.23 1720.96 L1971.23 1720.96 L1970.95 1720.96 L1970.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1970.95,1720.96 1970.95,1720.96 1971.23,1720.96 1970.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1971.23 1720.96 L1971.23 1720.96 L1971.51 1720.96 L1971.51 1720.96 L1971.23 1720.96 L1971.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1971.23,1720.96 1971.23,1720.96 1971.51,1720.96 1971.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1971.51 1720.96 L1971.51 1720.96 L1971.8 1720.96 L1971.8 1720.96 L1971.51 1720.96 L1971.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1971.51,1720.96 1971.51,1720.96 1971.8,1720.96 1971.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M1971.8 1720.96 L1971.8 1720.96 L1972.08 1720.96 L1972.08 1720.96 L1971.8 1720.96 L1971.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1971.8,1720.96 1971.8,1720.96 1972.08,1720.96 1971.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1972.08 1720.96 L1972.08 1720.96 L1972.36 1720.96 L1972.36 1720.96 L1972.08 1720.96 L1972.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1972.08,1720.96 1972.08,1720.96 1972.36,1720.96 1972.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1972.36 1720.96 L1972.36 1720.96 L1972.64 1720.96 L1972.64 1720.96 L1972.36 1720.96 L1972.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1972.36,1720.96 1972.36,1720.96 1972.64,1720.96 1972.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1972.64 1720.96 L1972.64 1720.96 L1972.92 1720.96 L1972.92 1720.96 L1972.64 1720.96 L1972.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1972.64,1720.96 1972.64,1720.96 1972.92,1720.96 1972.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1972.92 1720.96 L1972.92 1720.96 L1973.2 1720.96 L1973.2 1720.96 L1972.92 1720.96 L1972.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1972.92,1720.96 1972.92,1720.96 1973.2,1720.96 1972.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1973.2 1720.96 L1973.2 1720.96 L1973.49 1720.96 L1973.49 1720.96 L1973.2 1720.96 L1973.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1973.2,1720.96 1973.2,1720.96 1973.49,1720.96 1973.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M1973.49 1720.96 L1973.49 1720.96 L1973.77 1720.96 L1973.77 1720.96 L1973.49 1720.96 L1973.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1973.49,1720.96 1973.49,1720.96 1973.77,1720.96 1973.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1973.77 1720.96 L1973.77 1720.96 L1974.05 1720.96 L1974.05 1720.96 L1973.77 1720.96 L1973.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1973.77,1720.96 1973.77,1720.96 1974.05,1720.96 1973.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1974.05 1720.96 L1974.05 1720.96 L1974.33 1720.96 L1974.33 1720.96 L1974.05 1720.96 L1974.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1974.05,1720.96 1974.05,1720.96 1974.33,1720.96 1974.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1974.33 1720.96 L1974.33 1720.96 L1974.61 1720.96 L1974.61 1720.96 L1974.33 1720.96 L1974.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1974.33,1720.96 1974.33,1720.96 1974.61,1720.96 1974.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1974.61 1720.96 L1974.61 1720.96 L1974.89 1720.96 L1974.89 1720.96 L1974.61 1720.96 L1974.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1974.61,1720.96 1974.61,1720.96 1974.89,1720.96 1974.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M1974.89 1720.96 L1974.89 1720.96 L1975.18 1720.96 L1975.18 1720.96 L1974.89 1720.96 L1974.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1974.89,1720.96 1974.89,1720.96 1975.18,1720.96 1974.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M1975.18 1720.96 L1975.18 1720.96 L1975.46 1720.96 L1975.46 1720.96 L1975.18 1720.96 L1975.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1975.18,1720.96 1975.18,1720.96 1975.46,1720.96 1975.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1975.46 1720.96 L1975.46 1720.96 L1975.74 1720.96 L1975.74 1720.96 L1975.46 1720.96 L1975.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1975.46,1720.96 1975.46,1720.96 1975.74,1720.96 1975.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1975.74 1720.96 L1975.74 1720.96 L1976.02 1720.96 L1976.02 1720.96 L1975.74 1720.96 L1975.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1975.74,1720.96 1975.74,1720.96 1976.02,1720.96 1975.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1976.02 1720.96 L1976.02 1720.96 L1976.3 1720.96 L1976.3 1720.96 L1976.02 1720.96 L1976.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1976.02,1720.96 1976.02,1720.96 1976.3,1720.96 1976.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1976.3 1720.96 L1976.3 1720.96 L1976.58 1720.96 L1976.58 1720.96 L1976.3 1720.96 L1976.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1976.3,1720.96 1976.3,1720.96 1976.58,1720.96 1976.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M1976.58 1720.96 L1976.58 1720.96 L1976.87 1720.96 L1976.87 1720.96 L1976.58 1720.96 L1976.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1976.58,1720.96 1976.58,1720.96 1976.87,1720.96 1976.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M1976.87 1720.96 L1976.87 1720.96 L1977.15 1720.96 L1977.15 1720.96 L1976.87 1720.96 L1976.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1976.87,1720.96 1976.87,1720.96 1977.15,1720.96 1976.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1977.15 1720.96 L1977.15 1720.96 L1977.43 1720.96 L1977.43 1720.96 L1977.15 1720.96 L1977.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1977.15,1720.96 1977.15,1720.96 1977.43,1720.96 1977.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1977.43 1720.96 L1977.43 1720.96 L1977.71 1720.96 L1977.71 1720.96 L1977.43 1720.96 L1977.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1977.43,1720.96 1977.43,1720.96 1977.71,1720.96 1977.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1977.71 1720.96 L1977.71 1720.96 L1977.99 1720.96 L1977.99 1720.96 L1977.71 1720.96 L1977.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1977.71,1720.96 1977.71,1720.96 1977.99,1720.96 1977.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1977.99 1720.96 L1977.99 1720.96 L1978.27 1720.96 L1978.27 1720.96 L1977.99 1720.96 L1977.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1977.99,1720.96 1977.99,1720.96 1978.27,1720.96 1977.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M1978.27 1720.96 L1978.27 1720.96 L1978.56 1720.96 L1978.56 1720.96 L1978.27 1720.96 L1978.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1978.27,1720.96 1978.27,1720.96 1978.56,1720.96 1978.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M1978.56 1720.96 L1978.56 1720.96 L1978.84 1720.96 L1978.84 1720.96 L1978.56 1720.96 L1978.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1978.56,1720.96 1978.56,1720.96 1978.84,1720.96 1978.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1978.84 1720.96 L1978.84 1720.96 L1979.12 1720.96 L1979.12 1720.96 L1978.84 1720.96 L1978.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1978.84,1720.96 1978.84,1720.96 1979.12,1720.96 1978.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1979.12 1720.96 L1979.12 1720.96 L1979.4 1720.96 L1979.4 1720.96 L1979.12 1720.96 L1979.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1979.12,1720.96 1979.12,1720.96 1979.4,1720.96 1979.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1979.4 1720.96 L1979.4 1720.96 L1979.68 1720.96 L1979.68 1720.96 L1979.4 1720.96 L1979.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1979.4,1720.96 1979.4,1720.96 1979.68,1720.96 1979.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1979.68 1720.96 L1979.68 1720.96 L1979.97 1720.96 L1979.97 1720.96 L1979.68 1720.96 L1979.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1979.68,1720.96 1979.68,1720.96 1979.97,1720.96 1979.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M1979.97 1720.96 L1979.97 1720.96 L1980.25 1720.96 L1980.25 1720.96 L1979.97 1720.96 L1979.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1979.97,1720.96 1979.97,1720.96 1980.25,1720.96 1979.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M1980.25 1720.96 L1980.25 1720.96 L1980.53 1720.96 L1980.53 1720.96 L1980.25 1720.96 L1980.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1980.25,1720.96 1980.25,1720.96 1980.53,1720.96 1980.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M1980.53 1720.96 L1980.53 1720.96 L1980.81 1720.96 L1980.81 1720.96 L1980.53 1720.96 L1980.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1980.53,1720.96 1980.53,1720.96 1980.81,1720.96 1980.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M1980.81 1720.96 L1980.81 1720.96 L1981.09 1720.96 L1981.09 1720.96 L1980.81 1720.96 L1980.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1980.81,1720.96 1980.81,1720.96 1981.09,1720.96 1980.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M1981.09 1720.96 L1981.09 1720.96 L1981.37 1720.96 L1981.37 1720.96 L1981.09 1720.96 L1981.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1981.09,1720.96 1981.09,1720.96 1981.37,1720.96 1981.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M1981.37 1720.96 L1981.37 1720.96 L1981.66 1720.96 L1981.66 1720.96 L1981.37 1720.96 L1981.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1981.37,1720.96 1981.37,1720.96 1981.66,1720.96 1981.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M1981.66 1720.96 L1981.66 1720.96 L1981.94 1720.96 L1981.94 1720.96 L1981.66 1720.96 L1981.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1981.66,1720.96 1981.66,1720.96 1981.94,1720.96 1981.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M1981.94 1720.96 L1981.94 1720.96 L1982.22 1720.96 L1982.22 1720.96 L1981.94 1720.96 L1981.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1981.94,1720.96 1981.94,1720.96 1982.22,1720.96 1981.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M1982.22 1720.96 L1982.22 1720.96 L1982.5 1720.96 L1982.5 1720.96 L1982.22 1720.96 L1982.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1982.22,1720.96 1982.22,1720.96 1982.5,1720.96 1982.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M1982.5 1720.96 L1982.5 1720.96 L1982.78 1720.96 L1982.78 1720.96 L1982.5 1720.96 L1982.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1982.5,1720.96 1982.5,1720.96 1982.78,1720.96 1982.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M1982.78 1720.96 L1982.78 1720.96 L1983.06 1720.96 L1983.06 1720.96 L1982.78 1720.96 L1982.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1982.78,1720.96 1982.78,1720.96 1983.06,1720.96 1982.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M1983.06 1720.96 L1983.06 1720.96 L1983.35 1720.96 L1983.35 1720.96 L1983.06 1720.96 L1983.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1983.06,1720.96 1983.06,1720.96 1983.35,1720.96 1983.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M1983.35 1720.96 L1983.35 1720.96 L1983.63 1720.96 L1983.63 1720.96 L1983.35 1720.96 L1983.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1983.35,1720.96 1983.35,1720.96 1983.63,1720.96 1983.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M1983.63 1720.96 L1983.63 1720.96 L1983.91 1720.96 L1983.91 1720.96 L1983.63 1720.96 L1983.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1983.63,1720.96 1983.63,1720.96 1983.91,1720.96 1983.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M1983.91 1720.96 L1983.91 1720.96 L1984.19 1720.96 L1984.19 1720.96 L1983.91 1720.96 L1983.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1983.91,1720.96 1983.91,1720.96 1984.19,1720.96 1983.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M1984.19 1720.96 L1984.19 1720.96 L1984.47 1720.96 L1984.47 1720.96 L1984.19 1720.96 L1984.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1984.19,1720.96 1984.19,1720.96 1984.47,1720.96 1984.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M1984.47 1720.96 L1984.47 1720.96 L1984.75 1720.96 L1984.75 1720.96 L1984.47 1720.96 L1984.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1984.47,1720.96 1984.47,1720.96 1984.75,1720.96 1984.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M1984.75 1720.96 L1984.75 1720.96 L1985.04 1720.96 L1985.04 1720.96 L1984.75 1720.96 L1984.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1984.75,1720.96 1984.75,1720.96 1985.04,1720.96 1984.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M1985.04 1720.96 L1985.04 1720.96 L1985.32 1720.96 L1985.32 1720.96 L1985.04 1720.96 L1985.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1985.04,1720.96 1985.04,1720.96 1985.32,1720.96 1985.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M1985.32 1720.96 L1985.32 1720.96 L1985.6 1720.96 L1985.6 1720.96 L1985.32 1720.96 L1985.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1985.32,1720.96 1985.32,1720.96 1985.6,1720.96 1985.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M1985.6 1720.96 L1985.6 1720.96 L1985.88 1720.96 L1985.88 1720.96 L1985.6 1720.96 L1985.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1985.6,1720.96 1985.6,1720.96 1985.88,1720.96 1985.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M1985.88 1720.96 L1985.88 1720.96 L1986.16 1720.96 L1986.16 1720.96 L1985.88 1720.96 L1985.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1985.88,1720.96 1985.88,1720.96 1986.16,1720.96 1985.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M1986.16 1720.96 L1986.16 1720.96 L1986.45 1720.96 L1986.45 1720.96 L1986.16 1720.96 L1986.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1986.16,1720.96 1986.16,1720.96 1986.45,1720.96 1986.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M1986.45 1720.96 L1986.45 1720.96 L1986.73 1720.96 L1986.73 1720.96 L1986.45 1720.96 L1986.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1986.45,1720.96 1986.45,1720.96 1986.73,1720.96 1986.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M1986.73 1720.96 L1986.73 1720.96 L1987.01 1720.96 L1987.01 1720.96 L1986.73 1720.96 L1986.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1986.73,1720.96 1986.73,1720.96 1987.01,1720.96 1986.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M1987.01 1720.96 L1987.01 1720.96 L1987.29 1720.96 L1987.29 1720.96 L1987.01 1720.96 L1987.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1987.01,1720.96 1987.01,1720.96 1987.29,1720.96 1987.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M1987.29 1720.96 L1987.29 1720.96 L1987.57 1720.96 L1987.57 1720.96 L1987.29 1720.96 L1987.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1987.29,1720.96 1987.29,1720.96 1987.57,1720.96 1987.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M1987.57 1720.96 L1987.57 1720.96 L1987.85 1720.96 L1987.85 1720.96 L1987.57 1720.96 L1987.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1987.57,1720.96 1987.57,1720.96 1987.85,1720.96 1987.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M1987.85 1720.96 L1987.85 1720.96 L1988.14 1720.96 L1988.14 1720.96 L1987.85 1720.96 L1987.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1987.85,1720.96 1987.85,1720.96 1988.14,1720.96 1987.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M1988.14 1720.96 L1988.14 1720.96 L1988.42 1720.96 L1988.42 1720.96 L1988.14 1720.96 L1988.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1988.14,1720.96 1988.14,1720.96 1988.42,1720.96 1988.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M1988.42 1720.96 L1988.42 1720.96 L1988.7 1720.96 L1988.7 1720.96 L1988.42 1720.96 L1988.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1988.42,1720.96 1988.42,1720.96 1988.7,1720.96 1988.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M1988.7 1720.96 L1988.7 1720.96 L1988.98 1720.96 L1988.98 1720.96 L1988.7 1720.96 L1988.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1988.7,1720.96 1988.7,1720.96 1988.98,1720.96 1988.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M1988.98 1720.96 L1988.98 1720.96 L1989.26 1720.96 L1989.26 1720.96 L1988.98 1720.96 L1988.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1988.98,1720.96 1988.98,1720.96 1989.26,1720.96 1988.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M1989.26 1720.96 L1989.26 1720.96 L1989.54 1720.96 L1989.54 1720.96 L1989.26 1720.96 L1989.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1989.26,1720.96 1989.26,1720.96 1989.54,1720.96 1989.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M1989.54 1720.96 L1989.54 1720.96 L1989.83 1720.96 L1989.83 1720.96 L1989.54 1720.96 L1989.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1989.54,1720.96 1989.54,1720.96 1989.83,1720.96 1989.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M1989.83 1720.96 L1989.83 1720.96 L1990.11 1720.96 L1990.11 1720.96 L1989.83 1720.96 L1989.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1989.83,1720.96 1989.83,1720.96 1990.11,1720.96 1989.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M1990.11 1720.96 L1990.11 1720.96 L1990.39 1720.96 L1990.39 1720.96 L1990.11 1720.96 L1990.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1990.11,1720.96 1990.11,1720.96 1990.39,1720.96 1990.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M1990.39 1720.96 L1990.39 1720.96 L1990.67 1720.96 L1990.67 1720.96 L1990.39 1720.96 L1990.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1990.39,1720.96 1990.39,1720.96 1990.67,1720.96 1990.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M1990.67 1720.96 L1990.67 1720.96 L1990.95 1720.96 L1990.95 1720.96 L1990.67 1720.96 L1990.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1990.67,1720.96 1990.67,1720.96 1990.95,1720.96 1990.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M1990.95 1720.96 L1990.95 1720.96 L1991.23 1720.96 L1991.23 1720.96 L1990.95 1720.96 L1990.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1990.95,1720.96 1990.95,1720.96 1991.23,1720.96 1990.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M1991.23 1720.96 L1991.23 1720.96 L1991.52 1720.96 L1991.52 1720.96 L1991.23 1720.96 L1991.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1991.23,1720.96 1991.23,1720.96 1991.52,1720.96 1991.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M1991.52 1720.96 L1991.52 1720.96 L1991.8 1720.96 L1991.8 1720.96 L1991.52 1720.96 L1991.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1991.52,1720.96 1991.52,1720.96 1991.8,1720.96 1991.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M1991.8 1720.96 L1991.8 1720.96 L1992.08 1720.96 L1992.08 1720.96 L1991.8 1720.96 L1991.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1991.8,1720.96 1991.8,1720.96 1992.08,1720.96 1991.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M1992.08 1720.96 L1992.08 1720.96 L1992.36 1720.96 L1992.36 1720.96 L1992.08 1720.96 L1992.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1992.08,1720.96 1992.08,1720.96 1992.36,1720.96 1992.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M1992.36 1720.96 L1992.36 1720.96 L1992.64 1720.96 L1992.64 1720.96 L1992.36 1720.96 L1992.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1992.36,1720.96 1992.36,1720.96 1992.64,1720.96 1992.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M1992.64 1720.96 L1992.64 1720.96 L1992.92 1720.96 L1992.92 1720.96 L1992.64 1720.96 L1992.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1992.64,1720.96 1992.64,1720.96 1992.92,1720.96 1992.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M1992.92 1720.96 L1992.92 1720.96 L1993.21 1720.96 L1993.21 1720.96 L1992.92 1720.96 L1992.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1992.92,1720.96 1992.92,1720.96 1993.21,1720.96 1992.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M1993.21 1720.96 L1993.21 1720.96 L1993.49 1720.96 L1993.49 1720.96 L1993.21 1720.96 L1993.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1993.21,1720.96 1993.21,1720.96 1993.49,1720.96 1993.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M1993.49 1720.96 L1993.49 1720.96 L1993.77 1720.96 L1993.77 1720.96 L1993.49 1720.96 L1993.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1993.49,1720.96 1993.49,1720.96 1993.77,1720.96 1993.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M1993.77 1720.96 L1993.77 1720.96 L1994.05 1720.96 L1994.05 1720.96 L1993.77 1720.96 L1993.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1993.77,1720.96 1993.77,1720.96 1994.05,1720.96 1993.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M1994.05 1720.96 L1994.05 1720.96 L1994.33 1720.96 L1994.33 1720.96 L1994.05 1720.96 L1994.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1994.05,1720.96 1994.05,1720.96 1994.33,1720.96 1994.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M1994.33 1720.96 L1994.33 1720.96 L1994.62 1720.96 L1994.62 1720.96 L1994.33 1720.96 L1994.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1994.33,1720.96 1994.33,1720.96 1994.62,1720.96 1994.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M1994.62 1720.96 L1994.62 1720.96 L1994.9 1720.96 L1994.9 1720.96 L1994.62 1720.96 L1994.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1994.62,1720.96 1994.62,1720.96 1994.9,1720.96 1994.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M1994.9 1720.96 L1994.9 1720.96 L1995.18 1720.96 L1995.18 1720.96 L1994.9 1720.96 L1994.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1994.9,1720.96 1994.9,1720.96 1995.18,1720.96 1994.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M1995.18 1720.96 L1995.18 1720.96 L1995.46 1720.96 L1995.46 1720.96 L1995.18 1720.96 L1995.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1995.18,1720.96 1995.18,1720.96 1995.46,1720.96 1995.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M1995.46 1720.96 L1995.46 1720.96 L1995.74 1720.96 L1995.74 1720.96 L1995.46 1720.96 L1995.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1995.46,1720.96 1995.46,1720.96 1995.74,1720.96 1995.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M1995.74 1720.96 L1995.74 1720.96 L1996.02 1720.96 L1996.02 1720.96 L1995.74 1720.96 L1995.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1995.74,1720.96 1995.74,1720.96 1996.02,1720.96 1995.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M1996.02 1720.96 L1996.02 1720.96 L1996.31 1720.96 L1996.31 1720.96 L1996.02 1720.96 L1996.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1996.02,1720.96 1996.02,1720.96 1996.31,1720.96 1996.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M1996.31 1720.96 L1996.31 1720.96 L1996.59 1720.96 L1996.59 1720.96 L1996.31 1720.96 L1996.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1996.31,1720.96 1996.31,1720.96 1996.59,1720.96 1996.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M1996.59 1720.96 L1996.59 1720.96 L1996.87 1720.96 L1996.87 1720.96 L1996.59 1720.96 L1996.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1996.59,1720.96 1996.59,1720.96 1996.87,1720.96 1996.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M1996.87 1720.96 L1996.87 1720.96 L1997.15 1720.96 L1997.15 1720.96 L1996.87 1720.96 L1996.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1996.87,1720.96 1996.87,1720.96 1997.15,1720.96 1996.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M1997.15 1720.96 L1997.15 1720.96 L1997.43 1720.96 L1997.43 1720.96 L1997.15 1720.96 L1997.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1997.15,1720.96 1997.15,1720.96 1997.43,1720.96 1997.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M1997.43 1720.96 L1997.43 1720.96 L1997.71 1720.96 L1997.71 1720.96 L1997.43 1720.96 L1997.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1997.43,1720.96 1997.43,1720.96 1997.71,1720.96 1997.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M1997.71 1720.96 L1997.71 1720.96 L1998 1720.96 L1998 1720.96 L1997.71 1720.96 L1997.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1997.71,1720.96 1997.71,1720.96 1998,1720.96 1997.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M1998 1720.96 L1998 1720.96 L1998.28 1720.96 L1998.28 1720.96 L1998 1720.96 L1998 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1998,1720.96 1998,1720.96 1998.28,1720.96 1998,1720.96 "/>
<path clip-path="url(#clip322)" d="M1998.28 1720.96 L1998.28 1720.96 L1998.56 1720.96 L1998.56 1720.96 L1998.28 1720.96 L1998.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1998.28,1720.96 1998.28,1720.96 1998.56,1720.96 1998.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M1998.56 1720.96 L1998.56 1720.96 L1998.84 1720.96 L1998.84 1720.96 L1998.56 1720.96 L1998.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1998.56,1720.96 1998.56,1720.96 1998.84,1720.96 1998.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M1998.84 1720.96 L1998.84 1720.96 L1999.12 1720.96 L1999.12 1720.96 L1998.84 1720.96 L1998.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1998.84,1720.96 1998.84,1720.96 1999.12,1720.96 1998.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M1999.12 1720.96 L1999.12 1720.96 L1999.4 1720.96 L1999.4 1720.96 L1999.12 1720.96 L1999.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1999.12,1720.96 1999.12,1720.96 1999.4,1720.96 1999.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M1999.4 1720.96 L1999.4 1720.96 L1999.69 1720.96 L1999.69 1720.96 L1999.4 1720.96 L1999.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1999.4,1720.96 1999.4,1720.96 1999.69,1720.96 1999.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M1999.69 1720.96 L1999.69 1720.96 L1999.97 1720.96 L1999.97 1720.96 L1999.69 1720.96 L1999.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1999.69,1720.96 1999.69,1720.96 1999.97,1720.96 1999.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M1999.97 1720.96 L1999.97 1720.96 L2000.25 1720.96 L2000.25 1720.96 L1999.97 1720.96 L1999.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1999.97,1720.96 1999.97,1720.96 2000.25,1720.96 1999.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2000.25 1720.76 L2000.25 1720.96 L2000.53 1720.96 L2000.53 1720.76 L2000.25 1720.76 L2000.25 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2000.25,1720.76 2000.25,1720.96 2000.53,1720.96 2000.53,1720.76 2000.25,1720.76 "/>
<path clip-path="url(#clip322)" d="M2000.53 1720.96 L2000.53 1720.96 L2000.81 1720.96 L2000.81 1720.96 L2000.53 1720.96 L2000.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2000.53,1720.96 2000.53,1720.96 2000.81,1720.96 2000.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2000.81 1720.96 L2000.81 1720.96 L2001.09 1720.96 L2001.09 1720.96 L2000.81 1720.96 L2000.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2000.81,1720.96 2000.81,1720.96 2001.09,1720.96 2000.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2001.09 1720.96 L2001.09 1720.96 L2001.38 1720.96 L2001.38 1720.96 L2001.09 1720.96 L2001.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2001.09,1720.96 2001.09,1720.96 2001.38,1720.96 2001.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2001.38 1720.96 L2001.38 1720.96 L2001.66 1720.96 L2001.66 1720.96 L2001.38 1720.96 L2001.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2001.38,1720.96 2001.38,1720.96 2001.66,1720.96 2001.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2001.66 1720.96 L2001.66 1720.96 L2001.94 1720.96 L2001.94 1720.96 L2001.66 1720.96 L2001.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2001.66,1720.96 2001.66,1720.96 2001.94,1720.96 2001.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2001.94 1720.96 L2001.94 1720.96 L2002.22 1720.96 L2002.22 1720.96 L2001.94 1720.96 L2001.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2001.94,1720.96 2001.94,1720.96 2002.22,1720.96 2001.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2002.22 1720.96 L2002.22 1720.96 L2002.5 1720.96 L2002.5 1720.96 L2002.22 1720.96 L2002.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2002.22,1720.96 2002.22,1720.96 2002.5,1720.96 2002.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2002.5 1720.96 L2002.5 1720.96 L2002.79 1720.96 L2002.79 1720.96 L2002.5 1720.96 L2002.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2002.5,1720.96 2002.5,1720.96 2002.79,1720.96 2002.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2002.79 1720.96 L2002.79 1720.96 L2003.07 1720.96 L2003.07 1720.96 L2002.79 1720.96 L2002.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2002.79,1720.96 2002.79,1720.96 2003.07,1720.96 2002.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2003.07 1720.96 L2003.07 1720.96 L2003.35 1720.96 L2003.35 1720.96 L2003.07 1720.96 L2003.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2003.07,1720.96 2003.07,1720.96 2003.35,1720.96 2003.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2003.35 1720.96 L2003.35 1720.96 L2003.63 1720.96 L2003.63 1720.96 L2003.35 1720.96 L2003.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2003.35,1720.96 2003.35,1720.96 2003.63,1720.96 2003.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2003.63 1720.96 L2003.63 1720.96 L2003.91 1720.96 L2003.91 1720.96 L2003.63 1720.96 L2003.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2003.63,1720.96 2003.63,1720.96 2003.91,1720.96 2003.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2003.91 1720.96 L2003.91 1720.96 L2004.19 1720.96 L2004.19 1720.96 L2003.91 1720.96 L2003.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2003.91,1720.96 2003.91,1720.96 2004.19,1720.96 2003.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2004.19 1720.96 L2004.19 1720.96 L2004.48 1720.96 L2004.48 1720.96 L2004.19 1720.96 L2004.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2004.19,1720.96 2004.19,1720.96 2004.48,1720.96 2004.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2004.48 1720.96 L2004.48 1720.96 L2004.76 1720.96 L2004.76 1720.96 L2004.48 1720.96 L2004.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2004.48,1720.96 2004.48,1720.96 2004.76,1720.96 2004.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2004.76 1720.96 L2004.76 1720.96 L2005.04 1720.96 L2005.04 1720.96 L2004.76 1720.96 L2004.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2004.76,1720.96 2004.76,1720.96 2005.04,1720.96 2004.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2005.04 1720.96 L2005.04 1720.96 L2005.32 1720.96 L2005.32 1720.96 L2005.04 1720.96 L2005.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2005.04,1720.96 2005.04,1720.96 2005.32,1720.96 2005.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2005.32 1720.96 L2005.32 1720.96 L2005.6 1720.96 L2005.6 1720.96 L2005.32 1720.96 L2005.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2005.32,1720.96 2005.32,1720.96 2005.6,1720.96 2005.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2005.6 1720.96 L2005.6 1720.96 L2005.88 1720.96 L2005.88 1720.96 L2005.6 1720.96 L2005.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2005.6,1720.96 2005.6,1720.96 2005.88,1720.96 2005.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2005.88 1720.96 L2005.88 1720.96 L2006.17 1720.96 L2006.17 1720.96 L2005.88 1720.96 L2005.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2005.88,1720.96 2005.88,1720.96 2006.17,1720.96 2005.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2006.17 1720.96 L2006.17 1720.96 L2006.45 1720.96 L2006.45 1720.96 L2006.17 1720.96 L2006.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2006.17,1720.96 2006.17,1720.96 2006.45,1720.96 2006.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2006.45 1720.96 L2006.45 1720.96 L2006.73 1720.96 L2006.73 1720.96 L2006.45 1720.96 L2006.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2006.45,1720.96 2006.45,1720.96 2006.73,1720.96 2006.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2006.73 1720.96 L2006.73 1720.96 L2007.01 1720.96 L2007.01 1720.96 L2006.73 1720.96 L2006.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2006.73,1720.96 2006.73,1720.96 2007.01,1720.96 2006.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2007.01 1720.96 L2007.01 1720.96 L2007.29 1720.96 L2007.29 1720.96 L2007.01 1720.96 L2007.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2007.01,1720.96 2007.01,1720.96 2007.29,1720.96 2007.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2007.29 1720.96 L2007.29 1720.96 L2007.57 1720.96 L2007.57 1720.96 L2007.29 1720.96 L2007.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2007.29,1720.96 2007.29,1720.96 2007.57,1720.96 2007.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2007.57 1720.96 L2007.57 1720.96 L2007.86 1720.96 L2007.86 1720.96 L2007.57 1720.96 L2007.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2007.57,1720.96 2007.57,1720.96 2007.86,1720.96 2007.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2007.86 1720.96 L2007.86 1720.96 L2008.14 1720.96 L2008.14 1720.96 L2007.86 1720.96 L2007.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2007.86,1720.96 2007.86,1720.96 2008.14,1720.96 2007.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2008.14 1720.96 L2008.14 1720.96 L2008.42 1720.96 L2008.42 1720.96 L2008.14 1720.96 L2008.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2008.14,1720.96 2008.14,1720.96 2008.42,1720.96 2008.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2008.42 1720.96 L2008.42 1720.96 L2008.7 1720.96 L2008.7 1720.96 L2008.42 1720.96 L2008.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2008.42,1720.96 2008.42,1720.96 2008.7,1720.96 2008.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2008.7 1720.96 L2008.7 1720.96 L2008.98 1720.96 L2008.98 1720.96 L2008.7 1720.96 L2008.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2008.7,1720.96 2008.7,1720.96 2008.98,1720.96 2008.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2008.98 1720.96 L2008.98 1720.96 L2009.26 1720.96 L2009.26 1720.96 L2008.98 1720.96 L2008.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2008.98,1720.96 2008.98,1720.96 2009.26,1720.96 2008.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2009.26 1720.96 L2009.26 1720.96 L2009.55 1720.96 L2009.55 1720.96 L2009.26 1720.96 L2009.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2009.26,1720.96 2009.26,1720.96 2009.55,1720.96 2009.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2009.55 1720.96 L2009.55 1720.96 L2009.83 1720.96 L2009.83 1720.96 L2009.55 1720.96 L2009.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2009.55,1720.96 2009.55,1720.96 2009.83,1720.96 2009.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2009.83 1720.96 L2009.83 1720.96 L2010.11 1720.96 L2010.11 1720.96 L2009.83 1720.96 L2009.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2009.83,1720.96 2009.83,1720.96 2010.11,1720.96 2009.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2010.11 1720.96 L2010.11 1720.96 L2010.39 1720.96 L2010.39 1720.96 L2010.11 1720.96 L2010.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2010.11,1720.96 2010.11,1720.96 2010.39,1720.96 2010.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2010.39 1720.96 L2010.39 1720.96 L2010.67 1720.96 L2010.67 1720.96 L2010.39 1720.96 L2010.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2010.39,1720.96 2010.39,1720.96 2010.67,1720.96 2010.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2010.67 1720.96 L2010.67 1720.96 L2010.96 1720.96 L2010.96 1720.96 L2010.67 1720.96 L2010.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2010.67,1720.96 2010.67,1720.96 2010.96,1720.96 2010.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2010.96 1720.96 L2010.96 1720.96 L2011.24 1720.96 L2011.24 1720.96 L2010.96 1720.96 L2010.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2010.96,1720.96 2010.96,1720.96 2011.24,1720.96 2010.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2011.24 1720.96 L2011.24 1720.96 L2011.52 1720.96 L2011.52 1720.96 L2011.24 1720.96 L2011.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2011.24,1720.96 2011.24,1720.96 2011.52,1720.96 2011.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2011.52 1720.96 L2011.52 1720.96 L2011.8 1720.96 L2011.8 1720.96 L2011.52 1720.96 L2011.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2011.52,1720.96 2011.52,1720.96 2011.8,1720.96 2011.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2011.8 1720.96 L2011.8 1720.96 L2012.08 1720.96 L2012.08 1720.96 L2011.8 1720.96 L2011.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2011.8,1720.96 2011.8,1720.96 2012.08,1720.96 2011.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2012.08 1720.96 L2012.08 1720.96 L2012.36 1720.96 L2012.36 1720.96 L2012.08 1720.96 L2012.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2012.08,1720.96 2012.08,1720.96 2012.36,1720.96 2012.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2012.36 1720.96 L2012.36 1720.96 L2012.65 1720.96 L2012.65 1720.96 L2012.36 1720.96 L2012.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2012.36,1720.96 2012.36,1720.96 2012.65,1720.96 2012.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2012.65 1720.96 L2012.65 1720.96 L2012.93 1720.96 L2012.93 1720.96 L2012.65 1720.96 L2012.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2012.65,1720.96 2012.65,1720.96 2012.93,1720.96 2012.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2012.93 1720.96 L2012.93 1720.96 L2013.21 1720.96 L2013.21 1720.96 L2012.93 1720.96 L2012.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2012.93,1720.96 2012.93,1720.96 2013.21,1720.96 2012.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2013.21 1720.96 L2013.21 1720.96 L2013.49 1720.96 L2013.49 1720.96 L2013.21 1720.96 L2013.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2013.21,1720.96 2013.21,1720.96 2013.49,1720.96 2013.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2013.49 1720.96 L2013.49 1720.96 L2013.77 1720.96 L2013.77 1720.96 L2013.49 1720.96 L2013.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2013.49,1720.96 2013.49,1720.96 2013.77,1720.96 2013.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2013.77 1720.96 L2013.77 1720.96 L2014.05 1720.96 L2014.05 1720.96 L2013.77 1720.96 L2013.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2013.77,1720.96 2013.77,1720.96 2014.05,1720.96 2013.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2014.05 1720.96 L2014.05 1720.96 L2014.34 1720.96 L2014.34 1720.96 L2014.05 1720.96 L2014.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2014.05,1720.96 2014.05,1720.96 2014.34,1720.96 2014.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2014.34 1720.96 L2014.34 1720.96 L2014.62 1720.96 L2014.62 1720.96 L2014.34 1720.96 L2014.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2014.34,1720.96 2014.34,1720.96 2014.62,1720.96 2014.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2014.62 1720.96 L2014.62 1720.96 L2014.9 1720.96 L2014.9 1720.96 L2014.62 1720.96 L2014.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2014.62,1720.96 2014.62,1720.96 2014.9,1720.96 2014.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2014.9 1720.96 L2014.9 1720.96 L2015.18 1720.96 L2015.18 1720.96 L2014.9 1720.96 L2014.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2014.9,1720.96 2014.9,1720.96 2015.18,1720.96 2014.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2015.18 1720.96 L2015.18 1720.96 L2015.46 1720.96 L2015.46 1720.96 L2015.18 1720.96 L2015.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2015.18,1720.96 2015.18,1720.96 2015.46,1720.96 2015.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2015.46 1720.96 L2015.46 1720.96 L2015.74 1720.96 L2015.74 1720.96 L2015.46 1720.96 L2015.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2015.46,1720.96 2015.46,1720.96 2015.74,1720.96 2015.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2015.74 1720.96 L2015.74 1720.96 L2016.03 1720.96 L2016.03 1720.96 L2015.74 1720.96 L2015.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2015.74,1720.96 2015.74,1720.96 2016.03,1720.96 2015.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2016.03 1720.96 L2016.03 1720.96 L2016.31 1720.96 L2016.31 1720.96 L2016.03 1720.96 L2016.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2016.03,1720.96 2016.03,1720.96 2016.31,1720.96 2016.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2016.31 1720.96 L2016.31 1720.96 L2016.59 1720.96 L2016.59 1720.96 L2016.31 1720.96 L2016.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2016.31,1720.96 2016.31,1720.96 2016.59,1720.96 2016.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2016.59 1720.96 L2016.59 1720.96 L2016.87 1720.96 L2016.87 1720.96 L2016.59 1720.96 L2016.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2016.59,1720.96 2016.59,1720.96 2016.87,1720.96 2016.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2016.87 1720.96 L2016.87 1720.96 L2017.15 1720.96 L2017.15 1720.96 L2016.87 1720.96 L2016.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2016.87,1720.96 2016.87,1720.96 2017.15,1720.96 2016.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2017.15 1720.96 L2017.15 1720.96 L2017.43 1720.96 L2017.43 1720.96 L2017.15 1720.96 L2017.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2017.15,1720.96 2017.15,1720.96 2017.43,1720.96 2017.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2017.43 1720.96 L2017.43 1720.96 L2017.72 1720.96 L2017.72 1720.96 L2017.43 1720.96 L2017.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2017.43,1720.96 2017.43,1720.96 2017.72,1720.96 2017.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2017.72 1720.96 L2017.72 1720.96 L2018 1720.96 L2018 1720.96 L2017.72 1720.96 L2017.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2017.72,1720.96 2017.72,1720.96 2018,1720.96 2017.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2018 1720.96 L2018 1720.96 L2018.28 1720.96 L2018.28 1720.96 L2018 1720.96 L2018 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2018,1720.96 2018,1720.96 2018.28,1720.96 2018,1720.96 "/>
<path clip-path="url(#clip322)" d="M2018.28 1720.96 L2018.28 1720.96 L2018.56 1720.96 L2018.56 1720.96 L2018.28 1720.96 L2018.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2018.28,1720.96 2018.28,1720.96 2018.56,1720.96 2018.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2018.56 1720.96 L2018.56 1720.96 L2018.84 1720.96 L2018.84 1720.96 L2018.56 1720.96 L2018.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2018.56,1720.96 2018.56,1720.96 2018.84,1720.96 2018.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2018.84 1720.96 L2018.84 1720.96 L2019.13 1720.96 L2019.13 1720.96 L2018.84 1720.96 L2018.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2018.84,1720.96 2018.84,1720.96 2019.13,1720.96 2018.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2019.13 1720.96 L2019.13 1720.96 L2019.41 1720.96 L2019.41 1720.96 L2019.13 1720.96 L2019.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2019.13,1720.96 2019.13,1720.96 2019.41,1720.96 2019.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2019.41 1720.96 L2019.41 1720.96 L2019.69 1720.96 L2019.69 1720.96 L2019.41 1720.96 L2019.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2019.41,1720.96 2019.41,1720.96 2019.69,1720.96 2019.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2019.69 1720.96 L2019.69 1720.96 L2019.97 1720.96 L2019.97 1720.96 L2019.69 1720.96 L2019.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2019.69,1720.96 2019.69,1720.96 2019.97,1720.96 2019.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2019.97 1720.96 L2019.97 1720.96 L2020.25 1720.96 L2020.25 1720.96 L2019.97 1720.96 L2019.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2019.97,1720.96 2019.97,1720.96 2020.25,1720.96 2019.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2020.25 1720.96 L2020.25 1720.96 L2020.53 1720.96 L2020.53 1720.96 L2020.25 1720.96 L2020.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2020.25,1720.96 2020.25,1720.96 2020.53,1720.96 2020.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2020.53 1720.96 L2020.53 1720.96 L2020.82 1720.96 L2020.82 1720.96 L2020.53 1720.96 L2020.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2020.53,1720.96 2020.53,1720.96 2020.82,1720.96 2020.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2020.82 1720.96 L2020.82 1720.96 L2021.1 1720.96 L2021.1 1720.96 L2020.82 1720.96 L2020.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2020.82,1720.96 2020.82,1720.96 2021.1,1720.96 2020.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2021.1 1720.96 L2021.1 1720.96 L2021.38 1720.96 L2021.38 1720.96 L2021.1 1720.96 L2021.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2021.1,1720.96 2021.1,1720.96 2021.38,1720.96 2021.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2021.38 1720.96 L2021.38 1720.96 L2021.66 1720.96 L2021.66 1720.96 L2021.38 1720.96 L2021.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2021.38,1720.96 2021.38,1720.96 2021.66,1720.96 2021.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2021.66 1720.96 L2021.66 1720.96 L2021.94 1720.96 L2021.94 1720.96 L2021.66 1720.96 L2021.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2021.66,1720.96 2021.66,1720.96 2021.94,1720.96 2021.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2021.94 1720.96 L2021.94 1720.96 L2022.22 1720.96 L2022.22 1720.96 L2021.94 1720.96 L2021.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2021.94,1720.96 2021.94,1720.96 2022.22,1720.96 2021.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2022.22 1720.96 L2022.22 1720.96 L2022.51 1720.96 L2022.51 1720.96 L2022.22 1720.96 L2022.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2022.22,1720.96 2022.22,1720.96 2022.51,1720.96 2022.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2022.51 1720.96 L2022.51 1720.96 L2022.79 1720.96 L2022.79 1720.96 L2022.51 1720.96 L2022.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2022.51,1720.96 2022.51,1720.96 2022.79,1720.96 2022.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2022.79 1720.96 L2022.79 1720.96 L2023.07 1720.96 L2023.07 1720.96 L2022.79 1720.96 L2022.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2022.79,1720.96 2022.79,1720.96 2023.07,1720.96 2022.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2023.07 1720.96 L2023.07 1720.96 L2023.35 1720.96 L2023.35 1720.96 L2023.07 1720.96 L2023.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2023.07,1720.96 2023.07,1720.96 2023.35,1720.96 2023.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2023.35 1720.96 L2023.35 1720.96 L2023.63 1720.96 L2023.63 1720.96 L2023.35 1720.96 L2023.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2023.35,1720.96 2023.35,1720.96 2023.63,1720.96 2023.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2023.63 1720.96 L2023.63 1720.96 L2023.91 1720.96 L2023.91 1720.96 L2023.63 1720.96 L2023.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2023.63,1720.96 2023.63,1720.96 2023.91,1720.96 2023.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2023.91 1720.96 L2023.91 1720.96 L2024.2 1720.96 L2024.2 1720.96 L2023.91 1720.96 L2023.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2023.91,1720.96 2023.91,1720.96 2024.2,1720.96 2023.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2024.2 1720.96 L2024.2 1720.96 L2024.48 1720.96 L2024.48 1720.96 L2024.2 1720.96 L2024.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2024.2,1720.96 2024.2,1720.96 2024.48,1720.96 2024.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2024.48 1720.96 L2024.48 1720.96 L2024.76 1720.96 L2024.76 1720.96 L2024.48 1720.96 L2024.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2024.48,1720.96 2024.48,1720.96 2024.76,1720.96 2024.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2024.76 1720.96 L2024.76 1720.96 L2025.04 1720.96 L2025.04 1720.96 L2024.76 1720.96 L2024.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2024.76,1720.96 2024.76,1720.96 2025.04,1720.96 2024.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2025.04 1720.96 L2025.04 1720.96 L2025.32 1720.96 L2025.32 1720.96 L2025.04 1720.96 L2025.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2025.04,1720.96 2025.04,1720.96 2025.32,1720.96 2025.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2025.32 1720.96 L2025.32 1720.96 L2025.6 1720.96 L2025.6 1720.96 L2025.32 1720.96 L2025.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2025.32,1720.96 2025.32,1720.96 2025.6,1720.96 2025.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2025.6 1720.96 L2025.6 1720.96 L2025.89 1720.96 L2025.89 1720.96 L2025.6 1720.96 L2025.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2025.6,1720.96 2025.6,1720.96 2025.89,1720.96 2025.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2025.89 1720.96 L2025.89 1720.96 L2026.17 1720.96 L2026.17 1720.96 L2025.89 1720.96 L2025.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2025.89,1720.96 2025.89,1720.96 2026.17,1720.96 2025.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2026.17 1720.96 L2026.17 1720.96 L2026.45 1720.96 L2026.45 1720.96 L2026.17 1720.96 L2026.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2026.17,1720.96 2026.17,1720.96 2026.45,1720.96 2026.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2026.45 1720.96 L2026.45 1720.96 L2026.73 1720.96 L2026.73 1720.96 L2026.45 1720.96 L2026.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2026.45,1720.96 2026.45,1720.96 2026.73,1720.96 2026.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2026.73 1720.96 L2026.73 1720.96 L2027.01 1720.96 L2027.01 1720.96 L2026.73 1720.96 L2026.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2026.73,1720.96 2026.73,1720.96 2027.01,1720.96 2026.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2027.01 1720.96 L2027.01 1720.96 L2027.3 1720.96 L2027.3 1720.96 L2027.01 1720.96 L2027.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2027.01,1720.96 2027.01,1720.96 2027.3,1720.96 2027.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2027.3 1720.96 L2027.3 1720.96 L2027.58 1720.96 L2027.58 1720.96 L2027.3 1720.96 L2027.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2027.3,1720.96 2027.3,1720.96 2027.58,1720.96 2027.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2027.58 1720.96 L2027.58 1720.96 L2027.86 1720.96 L2027.86 1720.96 L2027.58 1720.96 L2027.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2027.58,1720.96 2027.58,1720.96 2027.86,1720.96 2027.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2027.86 1720.96 L2027.86 1720.96 L2028.14 1720.96 L2028.14 1720.96 L2027.86 1720.96 L2027.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2027.86,1720.96 2027.86,1720.96 2028.14,1720.96 2027.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2028.14 1720.96 L2028.14 1720.96 L2028.42 1720.96 L2028.42 1720.96 L2028.14 1720.96 L2028.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2028.14,1720.96 2028.14,1720.96 2028.42,1720.96 2028.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2028.42 1720.96 L2028.42 1720.96 L2028.7 1720.96 L2028.7 1720.96 L2028.42 1720.96 L2028.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2028.42,1720.96 2028.42,1720.96 2028.7,1720.96 2028.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2028.7 1720.96 L2028.7 1720.96 L2028.99 1720.96 L2028.99 1720.96 L2028.7 1720.96 L2028.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2028.7,1720.96 2028.7,1720.96 2028.99,1720.96 2028.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2028.99 1720.96 L2028.99 1720.96 L2029.27 1720.96 L2029.27 1720.96 L2028.99 1720.96 L2028.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2028.99,1720.96 2028.99,1720.96 2029.27,1720.96 2028.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2029.27 1720.96 L2029.27 1720.96 L2029.55 1720.96 L2029.55 1720.96 L2029.27 1720.96 L2029.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2029.27,1720.96 2029.27,1720.96 2029.55,1720.96 2029.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2029.55 1720.96 L2029.55 1720.96 L2029.83 1720.96 L2029.83 1720.96 L2029.55 1720.96 L2029.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2029.55,1720.96 2029.55,1720.96 2029.83,1720.96 2029.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2029.83 1720.96 L2029.83 1720.96 L2030.11 1720.96 L2030.11 1720.96 L2029.83 1720.96 L2029.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2029.83,1720.96 2029.83,1720.96 2030.11,1720.96 2029.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2030.11 1720.96 L2030.11 1720.96 L2030.39 1720.96 L2030.39 1720.96 L2030.11 1720.96 L2030.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2030.11,1720.96 2030.11,1720.96 2030.39,1720.96 2030.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2030.39 1720.96 L2030.39 1720.96 L2030.68 1720.96 L2030.68 1720.96 L2030.39 1720.96 L2030.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2030.39,1720.96 2030.39,1720.96 2030.68,1720.96 2030.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2030.68 1720.96 L2030.68 1720.96 L2030.96 1720.96 L2030.96 1720.96 L2030.68 1720.96 L2030.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2030.68,1720.96 2030.68,1720.96 2030.96,1720.96 2030.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2030.96 1720.96 L2030.96 1720.96 L2031.24 1720.96 L2031.24 1720.96 L2030.96 1720.96 L2030.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2030.96,1720.96 2030.96,1720.96 2031.24,1720.96 2030.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2031.24 1720.96 L2031.24 1720.96 L2031.52 1720.96 L2031.52 1720.96 L2031.24 1720.96 L2031.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2031.24,1720.96 2031.24,1720.96 2031.52,1720.96 2031.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2031.52 1720.96 L2031.52 1720.96 L2031.8 1720.96 L2031.8 1720.96 L2031.52 1720.96 L2031.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2031.52,1720.96 2031.52,1720.96 2031.8,1720.96 2031.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2031.8 1720.96 L2031.8 1720.96 L2032.08 1720.96 L2032.08 1720.96 L2031.8 1720.96 L2031.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2031.8,1720.96 2031.8,1720.96 2032.08,1720.96 2031.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2032.08 1720.96 L2032.08 1720.96 L2032.37 1720.96 L2032.37 1720.96 L2032.08 1720.96 L2032.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2032.08,1720.96 2032.08,1720.96 2032.37,1720.96 2032.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2032.37 1720.96 L2032.37 1720.96 L2032.65 1720.96 L2032.65 1720.96 L2032.37 1720.96 L2032.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2032.37,1720.96 2032.37,1720.96 2032.65,1720.96 2032.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2032.65 1720.96 L2032.65 1720.96 L2032.93 1720.96 L2032.93 1720.96 L2032.65 1720.96 L2032.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2032.65,1720.96 2032.65,1720.96 2032.93,1720.96 2032.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2032.93 1720.96 L2032.93 1720.96 L2033.21 1720.96 L2033.21 1720.96 L2032.93 1720.96 L2032.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2032.93,1720.96 2032.93,1720.96 2033.21,1720.96 2032.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2033.21 1720.96 L2033.21 1720.96 L2033.49 1720.96 L2033.49 1720.96 L2033.21 1720.96 L2033.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2033.21,1720.96 2033.21,1720.96 2033.49,1720.96 2033.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2033.49 1720.96 L2033.49 1720.96 L2033.77 1720.96 L2033.77 1720.96 L2033.49 1720.96 L2033.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2033.49,1720.96 2033.49,1720.96 2033.77,1720.96 2033.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2033.77 1720.96 L2033.77 1720.96 L2034.06 1720.96 L2034.06 1720.96 L2033.77 1720.96 L2033.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2033.77,1720.96 2033.77,1720.96 2034.06,1720.96 2033.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2034.06 1720.96 L2034.06 1720.96 L2034.34 1720.96 L2034.34 1720.96 L2034.06 1720.96 L2034.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2034.06,1720.96 2034.06,1720.96 2034.34,1720.96 2034.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2034.34 1720.96 L2034.34 1720.96 L2034.62 1720.96 L2034.62 1720.96 L2034.34 1720.96 L2034.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2034.34,1720.96 2034.34,1720.96 2034.62,1720.96 2034.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2034.62 1720.96 L2034.62 1720.96 L2034.9 1720.96 L2034.9 1720.96 L2034.62 1720.96 L2034.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2034.62,1720.96 2034.62,1720.96 2034.9,1720.96 2034.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2034.9 1720.96 L2034.9 1720.96 L2035.18 1720.96 L2035.18 1720.96 L2034.9 1720.96 L2034.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2034.9,1720.96 2034.9,1720.96 2035.18,1720.96 2034.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2035.18 1720.96 L2035.18 1720.96 L2035.47 1720.96 L2035.47 1720.96 L2035.18 1720.96 L2035.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2035.18,1720.96 2035.18,1720.96 2035.47,1720.96 2035.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2035.47 1720.96 L2035.47 1720.96 L2035.75 1720.96 L2035.75 1720.96 L2035.47 1720.96 L2035.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2035.47,1720.96 2035.47,1720.96 2035.75,1720.96 2035.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2035.75 1720.96 L2035.75 1720.96 L2036.03 1720.96 L2036.03 1720.96 L2035.75 1720.96 L2035.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2035.75,1720.96 2035.75,1720.96 2036.03,1720.96 2035.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2036.03 1720.96 L2036.03 1720.96 L2036.31 1720.96 L2036.31 1720.96 L2036.03 1720.96 L2036.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2036.03,1720.96 2036.03,1720.96 2036.31,1720.96 2036.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2036.31 1720.96 L2036.31 1720.96 L2036.59 1720.96 L2036.59 1720.96 L2036.31 1720.96 L2036.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2036.31,1720.96 2036.31,1720.96 2036.59,1720.96 2036.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2036.59 1720.96 L2036.59 1720.96 L2036.87 1720.96 L2036.87 1720.96 L2036.59 1720.96 L2036.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2036.59,1720.96 2036.59,1720.96 2036.87,1720.96 2036.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2036.87 1720.96 L2036.87 1720.96 L2037.16 1720.96 L2037.16 1720.96 L2036.87 1720.96 L2036.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2036.87,1720.96 2036.87,1720.96 2037.16,1720.96 2036.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2037.16 1720.96 L2037.16 1720.96 L2037.44 1720.96 L2037.44 1720.96 L2037.16 1720.96 L2037.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2037.16,1720.96 2037.16,1720.96 2037.44,1720.96 2037.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2037.44 1720.96 L2037.44 1720.96 L2037.72 1720.96 L2037.72 1720.96 L2037.44 1720.96 L2037.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2037.44,1720.96 2037.44,1720.96 2037.72,1720.96 2037.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2037.72 1720.96 L2037.72 1720.96 L2038 1720.96 L2038 1720.96 L2037.72 1720.96 L2037.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2037.72,1720.96 2037.72,1720.96 2038,1720.96 2037.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2038 1720.96 L2038 1720.96 L2038.28 1720.96 L2038.28 1720.96 L2038 1720.96 L2038 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2038,1720.96 2038,1720.96 2038.28,1720.96 2038,1720.96 "/>
<path clip-path="url(#clip322)" d="M2038.28 1720.96 L2038.28 1720.96 L2038.56 1720.96 L2038.56 1720.96 L2038.28 1720.96 L2038.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2038.28,1720.96 2038.28,1720.96 2038.56,1720.96 2038.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2038.56 1720.96 L2038.56 1720.96 L2038.85 1720.96 L2038.85 1720.96 L2038.56 1720.96 L2038.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2038.56,1720.96 2038.56,1720.96 2038.85,1720.96 2038.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2038.85 1720.96 L2038.85 1720.96 L2039.13 1720.96 L2039.13 1720.96 L2038.85 1720.96 L2038.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2038.85,1720.96 2038.85,1720.96 2039.13,1720.96 2038.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2039.13 1720.96 L2039.13 1720.96 L2039.41 1720.96 L2039.41 1720.96 L2039.13 1720.96 L2039.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2039.13,1720.96 2039.13,1720.96 2039.41,1720.96 2039.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2039.41 1720.96 L2039.41 1720.96 L2039.69 1720.96 L2039.69 1720.96 L2039.41 1720.96 L2039.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2039.41,1720.96 2039.41,1720.96 2039.69,1720.96 2039.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2039.69 1720.96 L2039.69 1720.96 L2039.97 1720.96 L2039.97 1720.96 L2039.69 1720.96 L2039.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2039.69,1720.96 2039.69,1720.96 2039.97,1720.96 2039.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2039.97 1720.96 L2039.97 1720.96 L2040.25 1720.96 L2040.25 1720.96 L2039.97 1720.96 L2039.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2039.97,1720.96 2039.97,1720.96 2040.25,1720.96 2039.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2040.25 1720.96 L2040.25 1720.96 L2040.54 1720.96 L2040.54 1720.96 L2040.25 1720.96 L2040.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2040.25,1720.96 2040.25,1720.96 2040.54,1720.96 2040.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2040.54 1720.96 L2040.54 1720.96 L2040.82 1720.96 L2040.82 1720.96 L2040.54 1720.96 L2040.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2040.54,1720.96 2040.54,1720.96 2040.82,1720.96 2040.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2040.82 1720.96 L2040.82 1720.96 L2041.1 1720.96 L2041.1 1720.96 L2040.82 1720.96 L2040.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2040.82,1720.96 2040.82,1720.96 2041.1,1720.96 2040.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2041.1 1720.96 L2041.1 1720.96 L2041.38 1720.96 L2041.38 1720.96 L2041.1 1720.96 L2041.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2041.1,1720.96 2041.1,1720.96 2041.38,1720.96 2041.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2041.38 1720.96 L2041.38 1720.96 L2041.66 1720.96 L2041.66 1720.96 L2041.38 1720.96 L2041.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2041.38,1720.96 2041.38,1720.96 2041.66,1720.96 2041.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2041.66 1720.96 L2041.66 1720.96 L2041.94 1720.96 L2041.94 1720.96 L2041.66 1720.96 L2041.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2041.66,1720.96 2041.66,1720.96 2041.94,1720.96 2041.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2041.94 1720.96 L2041.94 1720.96 L2042.23 1720.96 L2042.23 1720.96 L2041.94 1720.96 L2041.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2041.94,1720.96 2041.94,1720.96 2042.23,1720.96 2041.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2042.23 1720.96 L2042.23 1720.96 L2042.51 1720.96 L2042.51 1720.96 L2042.23 1720.96 L2042.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2042.23,1720.96 2042.23,1720.96 2042.51,1720.96 2042.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2042.51 1720.96 L2042.51 1720.96 L2042.79 1720.96 L2042.79 1720.96 L2042.51 1720.96 L2042.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2042.51,1720.96 2042.51,1720.96 2042.79,1720.96 2042.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2042.79 1720.96 L2042.79 1720.96 L2043.07 1720.96 L2043.07 1720.96 L2042.79 1720.96 L2042.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2042.79,1720.96 2042.79,1720.96 2043.07,1720.96 2042.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2043.07 1720.96 L2043.07 1720.96 L2043.35 1720.96 L2043.35 1720.96 L2043.07 1720.96 L2043.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2043.07,1720.96 2043.07,1720.96 2043.35,1720.96 2043.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2043.35 1720.96 L2043.35 1720.96 L2043.64 1720.96 L2043.64 1720.96 L2043.35 1720.96 L2043.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2043.35,1720.96 2043.35,1720.96 2043.64,1720.96 2043.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2043.64 1720.96 L2043.64 1720.96 L2043.92 1720.96 L2043.92 1720.96 L2043.64 1720.96 L2043.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2043.64,1720.96 2043.64,1720.96 2043.92,1720.96 2043.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2043.92 1720.96 L2043.92 1720.96 L2044.2 1720.96 L2044.2 1720.96 L2043.92 1720.96 L2043.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2043.92,1720.96 2043.92,1720.96 2044.2,1720.96 2043.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2044.2 1720.96 L2044.2 1720.96 L2044.48 1720.96 L2044.48 1720.96 L2044.2 1720.96 L2044.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2044.2,1720.96 2044.2,1720.96 2044.48,1720.96 2044.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2044.48 1720.96 L2044.48 1720.96 L2044.76 1720.96 L2044.76 1720.96 L2044.48 1720.96 L2044.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2044.48,1720.96 2044.48,1720.96 2044.76,1720.96 2044.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2044.76 1720.96 L2044.76 1720.96 L2045.04 1720.96 L2045.04 1720.96 L2044.76 1720.96 L2044.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2044.76,1720.96 2044.76,1720.96 2045.04,1720.96 2044.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2045.04 1720.96 L2045.04 1720.96 L2045.33 1720.96 L2045.33 1720.96 L2045.04 1720.96 L2045.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2045.04,1720.96 2045.04,1720.96 2045.33,1720.96 2045.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2045.33 1720.96 L2045.33 1720.96 L2045.61 1720.96 L2045.61 1720.96 L2045.33 1720.96 L2045.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2045.33,1720.96 2045.33,1720.96 2045.61,1720.96 2045.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2045.61 1720.96 L2045.61 1720.96 L2045.89 1720.96 L2045.89 1720.96 L2045.61 1720.96 L2045.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2045.61,1720.96 2045.61,1720.96 2045.89,1720.96 2045.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2045.89 1720.96 L2045.89 1720.96 L2046.17 1720.96 L2046.17 1720.96 L2045.89 1720.96 L2045.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2045.89,1720.96 2045.89,1720.96 2046.17,1720.96 2045.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2046.17 1720.96 L2046.17 1720.96 L2046.45 1720.96 L2046.45 1720.96 L2046.17 1720.96 L2046.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2046.17,1720.96 2046.17,1720.96 2046.45,1720.96 2046.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2046.45 1720.96 L2046.45 1720.96 L2046.73 1720.96 L2046.73 1720.96 L2046.45 1720.96 L2046.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2046.45,1720.96 2046.45,1720.96 2046.73,1720.96 2046.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2046.73 1720.96 L2046.73 1720.96 L2047.02 1720.96 L2047.02 1720.96 L2046.73 1720.96 L2046.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2046.73,1720.96 2046.73,1720.96 2047.02,1720.96 2046.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2047.02 1720.96 L2047.02 1720.96 L2047.3 1720.96 L2047.3 1720.96 L2047.02 1720.96 L2047.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2047.02,1720.96 2047.02,1720.96 2047.3,1720.96 2047.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2047.3 1720.96 L2047.3 1720.96 L2047.58 1720.96 L2047.58 1720.96 L2047.3 1720.96 L2047.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2047.3,1720.96 2047.3,1720.96 2047.58,1720.96 2047.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2047.58 1720.96 L2047.58 1720.96 L2047.86 1720.96 L2047.86 1720.96 L2047.58 1720.96 L2047.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2047.58,1720.96 2047.58,1720.96 2047.86,1720.96 2047.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2047.86 1720.96 L2047.86 1720.96 L2048.14 1720.96 L2048.14 1720.96 L2047.86 1720.96 L2047.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2047.86,1720.96 2047.86,1720.96 2048.14,1720.96 2047.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2048.14 1720.96 L2048.14 1720.96 L2048.42 1720.96 L2048.42 1720.96 L2048.14 1720.96 L2048.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2048.14,1720.96 2048.14,1720.96 2048.42,1720.96 2048.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2048.42 1720.96 L2048.42 1720.96 L2048.71 1720.96 L2048.71 1720.96 L2048.42 1720.96 L2048.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2048.42,1720.96 2048.42,1720.96 2048.71,1720.96 2048.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2048.71 1720.96 L2048.71 1720.96 L2048.99 1720.96 L2048.99 1720.96 L2048.71 1720.96 L2048.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2048.71,1720.96 2048.71,1720.96 2048.99,1720.96 2048.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2048.99 1720.96 L2048.99 1720.96 L2049.27 1720.96 L2049.27 1720.96 L2048.99 1720.96 L2048.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2048.99,1720.96 2048.99,1720.96 2049.27,1720.96 2048.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2049.27 1720.96 L2049.27 1720.96 L2049.55 1720.96 L2049.55 1720.96 L2049.27 1720.96 L2049.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2049.27,1720.96 2049.27,1720.96 2049.55,1720.96 2049.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2049.55 1720.96 L2049.55 1720.96 L2049.83 1720.96 L2049.83 1720.96 L2049.55 1720.96 L2049.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2049.55,1720.96 2049.55,1720.96 2049.83,1720.96 2049.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2049.83 1720.96 L2049.83 1720.96 L2050.12 1720.96 L2050.12 1720.96 L2049.83 1720.96 L2049.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2049.83,1720.96 2049.83,1720.96 2050.12,1720.96 2049.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2050.12 1720.96 L2050.12 1720.96 L2050.4 1720.96 L2050.4 1720.96 L2050.12 1720.96 L2050.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2050.12,1720.96 2050.12,1720.96 2050.4,1720.96 2050.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2050.4 1720.96 L2050.4 1720.96 L2050.68 1720.96 L2050.68 1720.96 L2050.4 1720.96 L2050.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2050.4,1720.96 2050.4,1720.96 2050.68,1720.96 2050.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2050.68 1720.96 L2050.68 1720.96 L2050.96 1720.96 L2050.96 1720.96 L2050.68 1720.96 L2050.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2050.68,1720.96 2050.68,1720.96 2050.96,1720.96 2050.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2050.96 1720.96 L2050.96 1720.96 L2051.24 1720.96 L2051.24 1720.96 L2050.96 1720.96 L2050.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2050.96,1720.96 2050.96,1720.96 2051.24,1720.96 2050.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2051.24 1720.96 L2051.24 1720.96 L2051.52 1720.96 L2051.52 1720.96 L2051.24 1720.96 L2051.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2051.24,1720.96 2051.24,1720.96 2051.52,1720.96 2051.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2051.52 1720.96 L2051.52 1720.96 L2051.81 1720.96 L2051.81 1720.96 L2051.52 1720.96 L2051.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2051.52,1720.96 2051.52,1720.96 2051.81,1720.96 2051.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2051.81 1720.96 L2051.81 1720.96 L2052.09 1720.96 L2052.09 1720.96 L2051.81 1720.96 L2051.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2051.81,1720.96 2051.81,1720.96 2052.09,1720.96 2051.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2052.09 1720.96 L2052.09 1720.96 L2052.37 1720.96 L2052.37 1720.96 L2052.09 1720.96 L2052.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2052.09,1720.96 2052.09,1720.96 2052.37,1720.96 2052.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2052.37 1720.96 L2052.37 1720.96 L2052.65 1720.96 L2052.65 1720.96 L2052.37 1720.96 L2052.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2052.37,1720.96 2052.37,1720.96 2052.65,1720.96 2052.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2052.65 1720.96 L2052.65 1720.96 L2052.93 1720.96 L2052.93 1720.96 L2052.65 1720.96 L2052.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2052.65,1720.96 2052.65,1720.96 2052.93,1720.96 2052.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2052.93 1720.96 L2052.93 1720.96 L2053.21 1720.96 L2053.21 1720.96 L2052.93 1720.96 L2052.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2052.93,1720.96 2052.93,1720.96 2053.21,1720.96 2052.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2053.21 1720.96 L2053.21 1720.96 L2053.5 1720.96 L2053.5 1720.96 L2053.21 1720.96 L2053.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2053.21,1720.96 2053.21,1720.96 2053.5,1720.96 2053.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2053.5 1720.96 L2053.5 1720.96 L2053.78 1720.96 L2053.78 1720.96 L2053.5 1720.96 L2053.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2053.5,1720.96 2053.5,1720.96 2053.78,1720.96 2053.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2053.78 1720.96 L2053.78 1720.96 L2054.06 1720.96 L2054.06 1720.96 L2053.78 1720.96 L2053.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2053.78,1720.96 2053.78,1720.96 2054.06,1720.96 2053.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2054.06 1720.96 L2054.06 1720.96 L2054.34 1720.96 L2054.34 1720.96 L2054.06 1720.96 L2054.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2054.06,1720.96 2054.06,1720.96 2054.34,1720.96 2054.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2054.34 1720.96 L2054.34 1720.96 L2054.62 1720.96 L2054.62 1720.96 L2054.34 1720.96 L2054.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2054.34,1720.96 2054.34,1720.96 2054.62,1720.96 2054.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2054.62 1720.96 L2054.62 1720.96 L2054.9 1720.96 L2054.9 1720.96 L2054.62 1720.96 L2054.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2054.62,1720.96 2054.62,1720.96 2054.9,1720.96 2054.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2054.9 1720.96 L2054.9 1720.96 L2055.19 1720.96 L2055.19 1720.96 L2054.9 1720.96 L2054.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2054.9,1720.96 2054.9,1720.96 2055.19,1720.96 2054.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2055.19 1720.96 L2055.19 1720.96 L2055.47 1720.96 L2055.47 1720.96 L2055.19 1720.96 L2055.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2055.19,1720.96 2055.19,1720.96 2055.47,1720.96 2055.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2055.47 1720.96 L2055.47 1720.96 L2055.75 1720.96 L2055.75 1720.96 L2055.47 1720.96 L2055.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2055.47,1720.96 2055.47,1720.96 2055.75,1720.96 2055.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2055.75 1720.96 L2055.75 1720.96 L2056.03 1720.96 L2056.03 1720.96 L2055.75 1720.96 L2055.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2055.75,1720.96 2055.75,1720.96 2056.03,1720.96 2055.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2056.03 1720.96 L2056.03 1720.96 L2056.31 1720.96 L2056.31 1720.96 L2056.03 1720.96 L2056.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2056.03,1720.96 2056.03,1720.96 2056.31,1720.96 2056.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2056.31 1720.96 L2056.31 1720.96 L2056.59 1720.96 L2056.59 1720.96 L2056.31 1720.96 L2056.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2056.31,1720.96 2056.31,1720.96 2056.59,1720.96 2056.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2056.59 1720.96 L2056.59 1720.96 L2056.88 1720.96 L2056.88 1720.96 L2056.59 1720.96 L2056.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2056.59,1720.96 2056.59,1720.96 2056.88,1720.96 2056.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2056.88 1720.96 L2056.88 1720.96 L2057.16 1720.96 L2057.16 1720.96 L2056.88 1720.96 L2056.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2056.88,1720.96 2056.88,1720.96 2057.16,1720.96 2056.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2057.16 1720.96 L2057.16 1720.96 L2057.44 1720.96 L2057.44 1720.96 L2057.16 1720.96 L2057.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2057.16,1720.96 2057.16,1720.96 2057.44,1720.96 2057.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2057.44 1720.96 L2057.44 1720.96 L2057.72 1720.96 L2057.72 1720.96 L2057.44 1720.96 L2057.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2057.44,1720.96 2057.44,1720.96 2057.72,1720.96 2057.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2057.72 1720.96 L2057.72 1720.96 L2058 1720.96 L2058 1720.96 L2057.72 1720.96 L2057.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2057.72,1720.96 2057.72,1720.96 2058,1720.96 2057.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2058 1720.96 L2058 1720.96 L2058.29 1720.96 L2058.29 1720.96 L2058 1720.96 L2058 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2058,1720.96 2058,1720.96 2058.29,1720.96 2058,1720.96 "/>
<path clip-path="url(#clip322)" d="M2058.29 1720.96 L2058.29 1720.96 L2058.57 1720.96 L2058.57 1720.96 L2058.29 1720.96 L2058.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2058.29,1720.96 2058.29,1720.96 2058.57,1720.96 2058.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2058.57 1720.96 L2058.57 1720.96 L2058.85 1720.96 L2058.85 1720.96 L2058.57 1720.96 L2058.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2058.57,1720.96 2058.57,1720.96 2058.85,1720.96 2058.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2058.85 1720.96 L2058.85 1720.96 L2059.13 1720.96 L2059.13 1720.96 L2058.85 1720.96 L2058.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2058.85,1720.96 2058.85,1720.96 2059.13,1720.96 2058.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2059.13 1720.96 L2059.13 1720.96 L2059.41 1720.96 L2059.41 1720.96 L2059.13 1720.96 L2059.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2059.13,1720.96 2059.13,1720.96 2059.41,1720.96 2059.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2059.41 1720.96 L2059.41 1720.96 L2059.69 1720.96 L2059.69 1720.96 L2059.41 1720.96 L2059.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2059.41,1720.96 2059.41,1720.96 2059.69,1720.96 2059.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2059.69 1720.96 L2059.69 1720.96 L2059.98 1720.96 L2059.98 1720.96 L2059.69 1720.96 L2059.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2059.69,1720.96 2059.69,1720.96 2059.98,1720.96 2059.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2059.98 1720.96 L2059.98 1720.96 L2060.26 1720.96 L2060.26 1720.96 L2059.98 1720.96 L2059.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2059.98,1720.96 2059.98,1720.96 2060.26,1720.96 2059.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2060.26 1720.96 L2060.26 1720.96 L2060.54 1720.96 L2060.54 1720.96 L2060.26 1720.96 L2060.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2060.26,1720.96 2060.26,1720.96 2060.54,1720.96 2060.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2060.54 1720.96 L2060.54 1720.96 L2060.82 1720.96 L2060.82 1720.96 L2060.54 1720.96 L2060.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2060.54,1720.96 2060.54,1720.96 2060.82,1720.96 2060.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2060.82 1720.96 L2060.82 1720.96 L2061.1 1720.96 L2061.1 1720.96 L2060.82 1720.96 L2060.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2060.82,1720.96 2060.82,1720.96 2061.1,1720.96 2060.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2061.1 1720.96 L2061.1 1720.96 L2061.38 1720.96 L2061.38 1720.96 L2061.1 1720.96 L2061.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2061.1,1720.96 2061.1,1720.96 2061.38,1720.96 2061.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2061.38 1720.96 L2061.38 1720.96 L2061.67 1720.96 L2061.67 1720.96 L2061.38 1720.96 L2061.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2061.38,1720.96 2061.38,1720.96 2061.67,1720.96 2061.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2061.67 1720.96 L2061.67 1720.96 L2061.95 1720.96 L2061.95 1720.96 L2061.67 1720.96 L2061.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2061.67,1720.96 2061.67,1720.96 2061.95,1720.96 2061.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2061.95 1720.96 L2061.95 1720.96 L2062.23 1720.96 L2062.23 1720.96 L2061.95 1720.96 L2061.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2061.95,1720.96 2061.95,1720.96 2062.23,1720.96 2061.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2062.23 1720.96 L2062.23 1720.96 L2062.51 1720.96 L2062.51 1720.96 L2062.23 1720.96 L2062.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2062.23,1720.96 2062.23,1720.96 2062.51,1720.96 2062.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2062.51 1720.96 L2062.51 1720.96 L2062.79 1720.96 L2062.79 1720.96 L2062.51 1720.96 L2062.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2062.51,1720.96 2062.51,1720.96 2062.79,1720.96 2062.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2062.79 1720.96 L2062.79 1720.96 L2063.07 1720.96 L2063.07 1720.96 L2062.79 1720.96 L2062.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2062.79,1720.96 2062.79,1720.96 2063.07,1720.96 2062.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2063.07 1720.96 L2063.07 1720.96 L2063.36 1720.96 L2063.36 1720.96 L2063.07 1720.96 L2063.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2063.07,1720.96 2063.07,1720.96 2063.36,1720.96 2063.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2063.36 1720.96 L2063.36 1720.96 L2063.64 1720.96 L2063.64 1720.96 L2063.36 1720.96 L2063.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2063.36,1720.96 2063.36,1720.96 2063.64,1720.96 2063.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2063.64 1720.96 L2063.64 1720.96 L2063.92 1720.96 L2063.92 1720.96 L2063.64 1720.96 L2063.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2063.64,1720.96 2063.64,1720.96 2063.92,1720.96 2063.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2063.92 1720.96 L2063.92 1720.96 L2064.2 1720.96 L2064.2 1720.96 L2063.92 1720.96 L2063.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2063.92,1720.96 2063.92,1720.96 2064.2,1720.96 2063.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2064.2 1720.96 L2064.2 1720.96 L2064.48 1720.96 L2064.48 1720.96 L2064.2 1720.96 L2064.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2064.2,1720.96 2064.2,1720.96 2064.48,1720.96 2064.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2064.48 1720.96 L2064.48 1720.96 L2064.76 1720.96 L2064.76 1720.96 L2064.48 1720.96 L2064.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2064.48,1720.96 2064.48,1720.96 2064.76,1720.96 2064.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2064.76 1720.96 L2064.76 1720.96 L2065.05 1720.96 L2065.05 1720.96 L2064.76 1720.96 L2064.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2064.76,1720.96 2064.76,1720.96 2065.05,1720.96 2064.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2065.05 1720.96 L2065.05 1720.96 L2065.33 1720.96 L2065.33 1720.96 L2065.05 1720.96 L2065.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2065.05,1720.96 2065.05,1720.96 2065.33,1720.96 2065.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2065.33 1720.96 L2065.33 1720.96 L2065.61 1720.96 L2065.61 1720.96 L2065.33 1720.96 L2065.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2065.33,1720.96 2065.33,1720.96 2065.61,1720.96 2065.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2065.61 1720.96 L2065.61 1720.96 L2065.89 1720.96 L2065.89 1720.96 L2065.61 1720.96 L2065.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2065.61,1720.96 2065.61,1720.96 2065.89,1720.96 2065.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2065.89 1720.96 L2065.89 1720.96 L2066.17 1720.96 L2066.17 1720.96 L2065.89 1720.96 L2065.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2065.89,1720.96 2065.89,1720.96 2066.17,1720.96 2065.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2066.17 1720.96 L2066.17 1720.96 L2066.46 1720.96 L2066.46 1720.96 L2066.17 1720.96 L2066.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2066.17,1720.96 2066.17,1720.96 2066.46,1720.96 2066.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2066.46 1720.96 L2066.46 1720.96 L2066.74 1720.96 L2066.74 1720.96 L2066.46 1720.96 L2066.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2066.46,1720.96 2066.46,1720.96 2066.74,1720.96 2066.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2066.74 1720.96 L2066.74 1720.96 L2067.02 1720.96 L2067.02 1720.96 L2066.74 1720.96 L2066.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2066.74,1720.96 2066.74,1720.96 2067.02,1720.96 2066.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2067.02 1720.96 L2067.02 1720.96 L2067.3 1720.96 L2067.3 1720.96 L2067.02 1720.96 L2067.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2067.02,1720.96 2067.02,1720.96 2067.3,1720.96 2067.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2067.3 1720.96 L2067.3 1720.96 L2067.58 1720.96 L2067.58 1720.96 L2067.3 1720.96 L2067.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2067.3,1720.96 2067.3,1720.96 2067.58,1720.96 2067.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2067.58 1720.96 L2067.58 1720.96 L2067.86 1720.96 L2067.86 1720.96 L2067.58 1720.96 L2067.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2067.58,1720.96 2067.58,1720.96 2067.86,1720.96 2067.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2067.86 1720.96 L2067.86 1720.96 L2068.15 1720.96 L2068.15 1720.96 L2067.86 1720.96 L2067.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2067.86,1720.96 2067.86,1720.96 2068.15,1720.96 2067.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2068.15 1720.96 L2068.15 1720.96 L2068.43 1720.96 L2068.43 1720.96 L2068.15 1720.96 L2068.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2068.15,1720.96 2068.15,1720.96 2068.43,1720.96 2068.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2068.43 1720.96 L2068.43 1720.96 L2068.71 1720.96 L2068.71 1720.96 L2068.43 1720.96 L2068.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2068.43,1720.96 2068.43,1720.96 2068.71,1720.96 2068.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2068.71 1720.96 L2068.71 1720.96 L2068.99 1720.96 L2068.99 1720.96 L2068.71 1720.96 L2068.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2068.71,1720.96 2068.71,1720.96 2068.99,1720.96 2068.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2068.99 1720.96 L2068.99 1720.96 L2069.27 1720.96 L2069.27 1720.96 L2068.99 1720.96 L2068.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2068.99,1720.96 2068.99,1720.96 2069.27,1720.96 2068.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2069.27 1720.96 L2069.27 1720.96 L2069.55 1720.96 L2069.55 1720.96 L2069.27 1720.96 L2069.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2069.27,1720.96 2069.27,1720.96 2069.55,1720.96 2069.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2069.55 1720.96 L2069.55 1720.96 L2069.84 1720.96 L2069.84 1720.96 L2069.55 1720.96 L2069.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2069.55,1720.96 2069.55,1720.96 2069.84,1720.96 2069.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2069.84 1720.96 L2069.84 1720.96 L2070.12 1720.96 L2070.12 1720.96 L2069.84 1720.96 L2069.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2069.84,1720.96 2069.84,1720.96 2070.12,1720.96 2069.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2070.12 1720.96 L2070.12 1720.96 L2070.4 1720.96 L2070.4 1720.96 L2070.12 1720.96 L2070.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2070.12,1720.96 2070.12,1720.96 2070.4,1720.96 2070.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2070.4 1720.96 L2070.4 1720.96 L2070.68 1720.96 L2070.68 1720.96 L2070.4 1720.96 L2070.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2070.4,1720.96 2070.4,1720.96 2070.68,1720.96 2070.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2070.68 1720.96 L2070.68 1720.96 L2070.96 1720.96 L2070.96 1720.96 L2070.68 1720.96 L2070.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2070.68,1720.96 2070.68,1720.96 2070.96,1720.96 2070.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2070.96 1720.96 L2070.96 1720.96 L2071.24 1720.96 L2071.24 1720.96 L2070.96 1720.96 L2070.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2070.96,1720.96 2070.96,1720.96 2071.24,1720.96 2070.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2071.24 1720.96 L2071.24 1720.96 L2071.53 1720.96 L2071.53 1720.96 L2071.24 1720.96 L2071.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2071.24,1720.96 2071.24,1720.96 2071.53,1720.96 2071.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2071.53 1720.96 L2071.53 1720.96 L2071.81 1720.96 L2071.81 1720.96 L2071.53 1720.96 L2071.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2071.53,1720.96 2071.53,1720.96 2071.81,1720.96 2071.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2071.81 1720.96 L2071.81 1720.96 L2072.09 1720.96 L2072.09 1720.96 L2071.81 1720.96 L2071.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2071.81,1720.96 2071.81,1720.96 2072.09,1720.96 2071.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2072.09 1720.96 L2072.09 1720.96 L2072.37 1720.96 L2072.37 1720.96 L2072.09 1720.96 L2072.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2072.09,1720.96 2072.09,1720.96 2072.37,1720.96 2072.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2072.37 1720.96 L2072.37 1720.96 L2072.65 1720.96 L2072.65 1720.96 L2072.37 1720.96 L2072.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2072.37,1720.96 2072.37,1720.96 2072.65,1720.96 2072.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2072.65 1720.96 L2072.65 1720.96 L2072.93 1720.96 L2072.93 1720.96 L2072.65 1720.96 L2072.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2072.65,1720.96 2072.65,1720.96 2072.93,1720.96 2072.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2072.93 1720.96 L2072.93 1720.96 L2073.22 1720.96 L2073.22 1720.96 L2072.93 1720.96 L2072.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2072.93,1720.96 2072.93,1720.96 2073.22,1720.96 2072.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2073.22 1720.96 L2073.22 1720.96 L2073.5 1720.96 L2073.5 1720.96 L2073.22 1720.96 L2073.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2073.22,1720.96 2073.22,1720.96 2073.5,1720.96 2073.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2073.5 1720.96 L2073.5 1720.96 L2073.78 1720.96 L2073.78 1720.96 L2073.5 1720.96 L2073.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2073.5,1720.96 2073.5,1720.96 2073.78,1720.96 2073.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2073.78 1720.96 L2073.78 1720.96 L2074.06 1720.96 L2074.06 1720.96 L2073.78 1720.96 L2073.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2073.78,1720.96 2073.78,1720.96 2074.06,1720.96 2073.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2074.06 1720.96 L2074.06 1720.96 L2074.34 1720.96 L2074.34 1720.96 L2074.06 1720.96 L2074.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2074.06,1720.96 2074.06,1720.96 2074.34,1720.96 2074.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2074.34 1720.96 L2074.34 1720.96 L2074.63 1720.96 L2074.63 1720.96 L2074.34 1720.96 L2074.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2074.34,1720.96 2074.34,1720.96 2074.63,1720.96 2074.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2074.63 1720.96 L2074.63 1720.96 L2074.91 1720.96 L2074.91 1720.96 L2074.63 1720.96 L2074.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2074.63,1720.96 2074.63,1720.96 2074.91,1720.96 2074.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2074.91 1720.96 L2074.91 1720.96 L2075.19 1720.96 L2075.19 1720.96 L2074.91 1720.96 L2074.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2074.91,1720.96 2074.91,1720.96 2075.19,1720.96 2074.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2075.19 1720.96 L2075.19 1720.96 L2075.47 1720.96 L2075.47 1720.96 L2075.19 1720.96 L2075.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2075.19,1720.96 2075.19,1720.96 2075.47,1720.96 2075.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2075.47 1720.96 L2075.47 1720.96 L2075.75 1720.96 L2075.75 1720.96 L2075.47 1720.96 L2075.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2075.47,1720.96 2075.47,1720.96 2075.75,1720.96 2075.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2075.75 1720.96 L2075.75 1720.96 L2076.03 1720.96 L2076.03 1720.96 L2075.75 1720.96 L2075.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2075.75,1720.96 2075.75,1720.96 2076.03,1720.96 2075.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2076.03 1720.96 L2076.03 1720.96 L2076.32 1720.96 L2076.32 1720.96 L2076.03 1720.96 L2076.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2076.03,1720.96 2076.03,1720.96 2076.32,1720.96 2076.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2076.32 1720.96 L2076.32 1720.96 L2076.6 1720.96 L2076.6 1720.96 L2076.32 1720.96 L2076.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2076.32,1720.96 2076.32,1720.96 2076.6,1720.96 2076.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2076.6 1720.96 L2076.6 1720.96 L2076.88 1720.96 L2076.88 1720.96 L2076.6 1720.96 L2076.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2076.6,1720.96 2076.6,1720.96 2076.88,1720.96 2076.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2076.88 1720.96 L2076.88 1720.96 L2077.16 1720.96 L2077.16 1720.96 L2076.88 1720.96 L2076.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2076.88,1720.96 2076.88,1720.96 2077.16,1720.96 2076.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2077.16 1720.96 L2077.16 1720.96 L2077.44 1720.96 L2077.44 1720.96 L2077.16 1720.96 L2077.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2077.16,1720.96 2077.16,1720.96 2077.44,1720.96 2077.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2077.44 1720.96 L2077.44 1720.96 L2077.72 1720.96 L2077.72 1720.96 L2077.44 1720.96 L2077.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2077.44,1720.96 2077.44,1720.96 2077.72,1720.96 2077.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2077.72 1720.96 L2077.72 1720.96 L2078.01 1720.96 L2078.01 1720.96 L2077.72 1720.96 L2077.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2077.72,1720.96 2077.72,1720.96 2078.01,1720.96 2077.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2078.01 1720.96 L2078.01 1720.96 L2078.29 1720.96 L2078.29 1720.96 L2078.01 1720.96 L2078.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2078.01,1720.96 2078.01,1720.96 2078.29,1720.96 2078.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2078.29 1720.96 L2078.29 1720.96 L2078.57 1720.96 L2078.57 1720.96 L2078.29 1720.96 L2078.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2078.29,1720.96 2078.29,1720.96 2078.57,1720.96 2078.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2078.57 1720.96 L2078.57 1720.96 L2078.85 1720.96 L2078.85 1720.96 L2078.57 1720.96 L2078.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2078.57,1720.96 2078.57,1720.96 2078.85,1720.96 2078.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2078.85 1720.96 L2078.85 1720.96 L2079.13 1720.96 L2079.13 1720.96 L2078.85 1720.96 L2078.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2078.85,1720.96 2078.85,1720.96 2079.13,1720.96 2078.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2079.13 1720.96 L2079.13 1720.96 L2079.41 1720.96 L2079.41 1720.96 L2079.13 1720.96 L2079.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2079.13,1720.96 2079.13,1720.96 2079.41,1720.96 2079.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2079.41 1720.96 L2079.41 1720.96 L2079.7 1720.96 L2079.7 1720.96 L2079.41 1720.96 L2079.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2079.41,1720.96 2079.41,1720.96 2079.7,1720.96 2079.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2079.7 1720.96 L2079.7 1720.96 L2079.98 1720.96 L2079.98 1720.96 L2079.7 1720.96 L2079.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2079.7,1720.96 2079.7,1720.96 2079.98,1720.96 2079.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2079.98 1720.96 L2079.98 1720.96 L2080.26 1720.96 L2080.26 1720.96 L2079.98 1720.96 L2079.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2079.98,1720.96 2079.98,1720.96 2080.26,1720.96 2079.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2080.26 1720.96 L2080.26 1720.96 L2080.54 1720.96 L2080.54 1720.96 L2080.26 1720.96 L2080.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2080.26,1720.96 2080.26,1720.96 2080.54,1720.96 2080.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2080.54 1720.96 L2080.54 1720.96 L2080.82 1720.96 L2080.82 1720.96 L2080.54 1720.96 L2080.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2080.54,1720.96 2080.54,1720.96 2080.82,1720.96 2080.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2080.82 1720.96 L2080.82 1720.96 L2081.1 1720.96 L2081.1 1720.96 L2080.82 1720.96 L2080.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2080.82,1720.96 2080.82,1720.96 2081.1,1720.96 2080.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2081.1 1720.96 L2081.1 1720.96 L2081.39 1720.96 L2081.39 1720.96 L2081.1 1720.96 L2081.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2081.1,1720.96 2081.1,1720.96 2081.39,1720.96 2081.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2081.39 1720.96 L2081.39 1720.96 L2081.67 1720.96 L2081.67 1720.96 L2081.39 1720.96 L2081.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2081.39,1720.96 2081.39,1720.96 2081.67,1720.96 2081.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2081.67 1720.96 L2081.67 1720.96 L2081.95 1720.96 L2081.95 1720.96 L2081.67 1720.96 L2081.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2081.67,1720.96 2081.67,1720.96 2081.95,1720.96 2081.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2081.95 1720.96 L2081.95 1720.96 L2082.23 1720.96 L2082.23 1720.96 L2081.95 1720.96 L2081.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2081.95,1720.96 2081.95,1720.96 2082.23,1720.96 2081.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2082.23 1720.96 L2082.23 1720.96 L2082.51 1720.96 L2082.51 1720.96 L2082.23 1720.96 L2082.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2082.23,1720.96 2082.23,1720.96 2082.51,1720.96 2082.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2082.51 1720.96 L2082.51 1720.96 L2082.8 1720.96 L2082.8 1720.96 L2082.51 1720.96 L2082.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2082.51,1720.96 2082.51,1720.96 2082.8,1720.96 2082.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2082.8 1720.96 L2082.8 1720.96 L2083.08 1720.96 L2083.08 1720.96 L2082.8 1720.96 L2082.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2082.8,1720.96 2082.8,1720.96 2083.08,1720.96 2082.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2083.08 1720.96 L2083.08 1720.96 L2083.36 1720.96 L2083.36 1720.96 L2083.08 1720.96 L2083.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2083.08,1720.96 2083.08,1720.96 2083.36,1720.96 2083.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2083.36 1720.96 L2083.36 1720.96 L2083.64 1720.96 L2083.64 1720.96 L2083.36 1720.96 L2083.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2083.36,1720.96 2083.36,1720.96 2083.64,1720.96 2083.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2083.64 1720.96 L2083.64 1720.96 L2083.92 1720.96 L2083.92 1720.96 L2083.64 1720.96 L2083.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2083.64,1720.96 2083.64,1720.96 2083.92,1720.96 2083.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2083.92 1720.96 L2083.92 1720.96 L2084.2 1720.96 L2084.2 1720.96 L2083.92 1720.96 L2083.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2083.92,1720.96 2083.92,1720.96 2084.2,1720.96 2083.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2084.2 1720.96 L2084.2 1720.96 L2084.49 1720.96 L2084.49 1720.96 L2084.2 1720.96 L2084.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2084.2,1720.96 2084.2,1720.96 2084.49,1720.96 2084.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2084.49 1720.96 L2084.49 1720.96 L2084.77 1720.96 L2084.77 1720.96 L2084.49 1720.96 L2084.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2084.49,1720.96 2084.49,1720.96 2084.77,1720.96 2084.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2084.77 1720.96 L2084.77 1720.96 L2085.05 1720.96 L2085.05 1720.96 L2084.77 1720.96 L2084.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2084.77,1720.96 2084.77,1720.96 2085.05,1720.96 2084.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2085.05 1720.96 L2085.05 1720.96 L2085.33 1720.96 L2085.33 1720.96 L2085.05 1720.96 L2085.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2085.05,1720.96 2085.05,1720.96 2085.33,1720.96 2085.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2085.33 1720.96 L2085.33 1720.96 L2085.61 1720.96 L2085.61 1720.96 L2085.33 1720.96 L2085.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2085.33,1720.96 2085.33,1720.96 2085.61,1720.96 2085.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2085.61 1720.96 L2085.61 1720.96 L2085.89 1720.96 L2085.89 1720.96 L2085.61 1720.96 L2085.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2085.61,1720.96 2085.61,1720.96 2085.89,1720.96 2085.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2085.89 1720.96 L2085.89 1720.96 L2086.18 1720.96 L2086.18 1720.96 L2085.89 1720.96 L2085.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2085.89,1720.96 2085.89,1720.96 2086.18,1720.96 2085.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2086.18 1720.96 L2086.18 1720.96 L2086.46 1720.96 L2086.46 1720.96 L2086.18 1720.96 L2086.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2086.18,1720.96 2086.18,1720.96 2086.46,1720.96 2086.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2086.46 1720.96 L2086.46 1720.96 L2086.74 1720.96 L2086.74 1720.96 L2086.46 1720.96 L2086.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2086.46,1720.96 2086.46,1720.96 2086.74,1720.96 2086.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2086.74 1720.96 L2086.74 1720.96 L2087.02 1720.96 L2087.02 1720.96 L2086.74 1720.96 L2086.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2086.74,1720.96 2086.74,1720.96 2087.02,1720.96 2086.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2087.02 1720.96 L2087.02 1720.96 L2087.3 1720.96 L2087.3 1720.96 L2087.02 1720.96 L2087.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2087.02,1720.96 2087.02,1720.96 2087.3,1720.96 2087.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2087.3 1720.96 L2087.3 1720.96 L2087.58 1720.96 L2087.58 1720.96 L2087.3 1720.96 L2087.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2087.3,1720.96 2087.3,1720.96 2087.58,1720.96 2087.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2087.58 1720.96 L2087.58 1720.96 L2087.87 1720.96 L2087.87 1720.96 L2087.58 1720.96 L2087.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2087.58,1720.96 2087.58,1720.96 2087.87,1720.96 2087.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2087.87 1720.96 L2087.87 1720.96 L2088.15 1720.96 L2088.15 1720.96 L2087.87 1720.96 L2087.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2087.87,1720.96 2087.87,1720.96 2088.15,1720.96 2087.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2088.15 1720.96 L2088.15 1720.96 L2088.43 1720.96 L2088.43 1720.96 L2088.15 1720.96 L2088.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2088.15,1720.96 2088.15,1720.96 2088.43,1720.96 2088.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2088.43 1720.96 L2088.43 1720.96 L2088.71 1720.96 L2088.71 1720.96 L2088.43 1720.96 L2088.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2088.43,1720.96 2088.43,1720.96 2088.71,1720.96 2088.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2088.71 1720.96 L2088.71 1720.96 L2088.99 1720.96 L2088.99 1720.96 L2088.71 1720.96 L2088.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2088.71,1720.96 2088.71,1720.96 2088.99,1720.96 2088.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2088.99 1720.96 L2088.99 1720.96 L2089.27 1720.96 L2089.27 1720.96 L2088.99 1720.96 L2088.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2088.99,1720.96 2088.99,1720.96 2089.27,1720.96 2088.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2089.27 1720.96 L2089.27 1720.96 L2089.56 1720.96 L2089.56 1720.96 L2089.27 1720.96 L2089.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2089.27,1720.96 2089.27,1720.96 2089.56,1720.96 2089.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2089.56 1720.96 L2089.56 1720.96 L2089.84 1720.96 L2089.84 1720.96 L2089.56 1720.96 L2089.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2089.56,1720.96 2089.56,1720.96 2089.84,1720.96 2089.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2089.84 1720.96 L2089.84 1720.96 L2090.12 1720.96 L2090.12 1720.96 L2089.84 1720.96 L2089.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2089.84,1720.96 2089.84,1720.96 2090.12,1720.96 2089.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2090.12 1720.96 L2090.12 1720.96 L2090.4 1720.96 L2090.4 1720.96 L2090.12 1720.96 L2090.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2090.12,1720.96 2090.12,1720.96 2090.4,1720.96 2090.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2090.4 1720.96 L2090.4 1720.96 L2090.68 1720.96 L2090.68 1720.96 L2090.4 1720.96 L2090.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2090.4,1720.96 2090.4,1720.96 2090.68,1720.96 2090.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2090.68 1720.96 L2090.68 1720.96 L2090.97 1720.96 L2090.97 1720.96 L2090.68 1720.96 L2090.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2090.68,1720.96 2090.68,1720.96 2090.97,1720.96 2090.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2090.97 1720.96 L2090.97 1720.96 L2091.25 1720.96 L2091.25 1720.96 L2090.97 1720.96 L2090.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2090.97,1720.96 2090.97,1720.96 2091.25,1720.96 2090.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2091.25 1720.96 L2091.25 1720.96 L2091.53 1720.96 L2091.53 1720.96 L2091.25 1720.96 L2091.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2091.25,1720.96 2091.25,1720.96 2091.53,1720.96 2091.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2091.53 1720.96 L2091.53 1720.96 L2091.81 1720.96 L2091.81 1720.96 L2091.53 1720.96 L2091.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2091.53,1720.96 2091.53,1720.96 2091.81,1720.96 2091.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2091.81 1720.96 L2091.81 1720.96 L2092.09 1720.96 L2092.09 1720.96 L2091.81 1720.96 L2091.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2091.81,1720.96 2091.81,1720.96 2092.09,1720.96 2091.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2092.09 1720.96 L2092.09 1720.96 L2092.37 1720.96 L2092.37 1720.96 L2092.09 1720.96 L2092.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2092.09,1720.96 2092.09,1720.96 2092.37,1720.96 2092.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2092.37 1720.96 L2092.37 1720.96 L2092.66 1720.96 L2092.66 1720.96 L2092.37 1720.96 L2092.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2092.37,1720.96 2092.37,1720.96 2092.66,1720.96 2092.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2092.66 1720.96 L2092.66 1720.96 L2092.94 1720.96 L2092.94 1720.96 L2092.66 1720.96 L2092.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2092.66,1720.96 2092.66,1720.96 2092.94,1720.96 2092.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2092.94 1720.96 L2092.94 1720.96 L2093.22 1720.96 L2093.22 1720.96 L2092.94 1720.96 L2092.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2092.94,1720.96 2092.94,1720.96 2093.22,1720.96 2092.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2093.22 1720.96 L2093.22 1720.96 L2093.5 1720.96 L2093.5 1720.96 L2093.22 1720.96 L2093.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2093.22,1720.96 2093.22,1720.96 2093.5,1720.96 2093.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2093.5 1720.96 L2093.5 1720.96 L2093.78 1720.96 L2093.78 1720.96 L2093.5 1720.96 L2093.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2093.5,1720.96 2093.5,1720.96 2093.78,1720.96 2093.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2093.78 1720.96 L2093.78 1720.96 L2094.06 1720.96 L2094.06 1720.96 L2093.78 1720.96 L2093.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2093.78,1720.96 2093.78,1720.96 2094.06,1720.96 2093.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2094.06 1720.96 L2094.06 1720.96 L2094.35 1720.96 L2094.35 1720.96 L2094.06 1720.96 L2094.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2094.06,1720.96 2094.06,1720.96 2094.35,1720.96 2094.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2094.35 1720.96 L2094.35 1720.96 L2094.63 1720.96 L2094.63 1720.96 L2094.35 1720.96 L2094.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2094.35,1720.96 2094.35,1720.96 2094.63,1720.96 2094.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2094.63 1720.96 L2094.63 1720.96 L2094.91 1720.96 L2094.91 1720.96 L2094.63 1720.96 L2094.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2094.63,1720.96 2094.63,1720.96 2094.91,1720.96 2094.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2094.91 1720.96 L2094.91 1720.96 L2095.19 1720.96 L2095.19 1720.96 L2094.91 1720.96 L2094.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2094.91,1720.96 2094.91,1720.96 2095.19,1720.96 2094.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2095.19 1720.96 L2095.19 1720.96 L2095.47 1720.96 L2095.47 1720.96 L2095.19 1720.96 L2095.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2095.19,1720.96 2095.19,1720.96 2095.47,1720.96 2095.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2095.47 1720.96 L2095.47 1720.96 L2095.75 1720.96 L2095.75 1720.96 L2095.47 1720.96 L2095.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2095.47,1720.96 2095.47,1720.96 2095.75,1720.96 2095.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2095.75 1720.96 L2095.75 1720.96 L2096.04 1720.96 L2096.04 1720.96 L2095.75 1720.96 L2095.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2095.75,1720.96 2095.75,1720.96 2096.04,1720.96 2095.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2096.04 1720.96 L2096.04 1720.96 L2096.32 1720.96 L2096.32 1720.96 L2096.04 1720.96 L2096.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2096.04,1720.96 2096.04,1720.96 2096.32,1720.96 2096.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2096.32 1720.96 L2096.32 1720.96 L2096.6 1720.96 L2096.6 1720.96 L2096.32 1720.96 L2096.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2096.32,1720.96 2096.32,1720.96 2096.6,1720.96 2096.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2096.6 1720.96 L2096.6 1720.96 L2096.88 1720.96 L2096.88 1720.96 L2096.6 1720.96 L2096.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2096.6,1720.96 2096.6,1720.96 2096.88,1720.96 2096.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2096.88 1720.96 L2096.88 1720.96 L2097.16 1720.96 L2097.16 1720.96 L2096.88 1720.96 L2096.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2096.88,1720.96 2096.88,1720.96 2097.16,1720.96 2096.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2097.16 1720.96 L2097.16 1720.96 L2097.44 1720.96 L2097.44 1720.96 L2097.16 1720.96 L2097.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2097.16,1720.96 2097.16,1720.96 2097.44,1720.96 2097.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2097.44 1720.96 L2097.44 1720.96 L2097.73 1720.96 L2097.73 1720.96 L2097.44 1720.96 L2097.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2097.44,1720.96 2097.44,1720.96 2097.73,1720.96 2097.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2097.73 1720.96 L2097.73 1720.96 L2098.01 1720.96 L2098.01 1720.96 L2097.73 1720.96 L2097.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2097.73,1720.96 2097.73,1720.96 2098.01,1720.96 2097.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2098.01 1720.96 L2098.01 1720.96 L2098.29 1720.96 L2098.29 1720.96 L2098.01 1720.96 L2098.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2098.01,1720.96 2098.01,1720.96 2098.29,1720.96 2098.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2098.29 1720.96 L2098.29 1720.96 L2098.57 1720.96 L2098.57 1720.96 L2098.29 1720.96 L2098.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2098.29,1720.96 2098.29,1720.96 2098.57,1720.96 2098.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2098.57 1720.96 L2098.57 1720.96 L2098.85 1720.96 L2098.85 1720.96 L2098.57 1720.96 L2098.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2098.57,1720.96 2098.57,1720.96 2098.85,1720.96 2098.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2098.85 1720.96 L2098.85 1720.96 L2099.14 1720.96 L2099.14 1720.96 L2098.85 1720.96 L2098.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2098.85,1720.96 2098.85,1720.96 2099.14,1720.96 2098.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2099.14 1720.96 L2099.14 1720.96 L2099.42 1720.96 L2099.42 1720.96 L2099.14 1720.96 L2099.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2099.14,1720.96 2099.14,1720.96 2099.42,1720.96 2099.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2099.42 1720.96 L2099.42 1720.96 L2099.7 1720.96 L2099.7 1720.96 L2099.42 1720.96 L2099.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2099.42,1720.96 2099.42,1720.96 2099.7,1720.96 2099.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2099.7 1720.96 L2099.7 1720.96 L2099.98 1720.96 L2099.98 1720.96 L2099.7 1720.96 L2099.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2099.7,1720.96 2099.7,1720.96 2099.98,1720.96 2099.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2099.98 1720.96 L2099.98 1720.96 L2100.26 1720.96 L2100.26 1720.96 L2099.98 1720.96 L2099.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2099.98,1720.96 2099.98,1720.96 2100.26,1720.96 2099.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2100.26 1720.96 L2100.26 1720.96 L2100.54 1720.96 L2100.54 1720.96 L2100.26 1720.96 L2100.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2100.26,1720.96 2100.26,1720.96 2100.54,1720.96 2100.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2100.54 1720.96 L2100.54 1720.96 L2100.83 1720.96 L2100.83 1720.96 L2100.54 1720.96 L2100.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2100.54,1720.96 2100.54,1720.96 2100.83,1720.96 2100.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2100.83 1720.96 L2100.83 1720.96 L2101.11 1720.96 L2101.11 1720.96 L2100.83 1720.96 L2100.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2100.83,1720.96 2100.83,1720.96 2101.11,1720.96 2100.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2101.11 1720.96 L2101.11 1720.96 L2101.39 1720.96 L2101.39 1720.96 L2101.11 1720.96 L2101.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2101.11,1720.96 2101.11,1720.96 2101.39,1720.96 2101.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2101.39 1720.96 L2101.39 1720.96 L2101.67 1720.96 L2101.67 1720.96 L2101.39 1720.96 L2101.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2101.39,1720.96 2101.39,1720.96 2101.67,1720.96 2101.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2101.67 1720.96 L2101.67 1720.96 L2101.95 1720.96 L2101.95 1720.96 L2101.67 1720.96 L2101.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2101.67,1720.96 2101.67,1720.96 2101.95,1720.96 2101.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2101.95 1720.96 L2101.95 1720.96 L2102.23 1720.96 L2102.23 1720.96 L2101.95 1720.96 L2101.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2101.95,1720.96 2101.95,1720.96 2102.23,1720.96 2101.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2102.23 1720.96 L2102.23 1720.96 L2102.52 1720.96 L2102.52 1720.96 L2102.23 1720.96 L2102.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2102.23,1720.96 2102.23,1720.96 2102.52,1720.96 2102.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2102.52 1720.96 L2102.52 1720.96 L2102.8 1720.96 L2102.8 1720.96 L2102.52 1720.96 L2102.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2102.52,1720.96 2102.52,1720.96 2102.8,1720.96 2102.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2102.8 1720.96 L2102.8 1720.96 L2103.08 1720.96 L2103.08 1720.96 L2102.8 1720.96 L2102.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2102.8,1720.96 2102.8,1720.96 2103.08,1720.96 2102.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2103.08 1720.96 L2103.08 1720.96 L2103.36 1720.96 L2103.36 1720.96 L2103.08 1720.96 L2103.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2103.08,1720.96 2103.08,1720.96 2103.36,1720.96 2103.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2103.36 1720.96 L2103.36 1720.96 L2103.64 1720.96 L2103.64 1720.96 L2103.36 1720.96 L2103.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2103.36,1720.96 2103.36,1720.96 2103.64,1720.96 2103.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2103.64 1720.96 L2103.64 1720.96 L2103.92 1720.96 L2103.92 1720.96 L2103.64 1720.96 L2103.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2103.64,1720.96 2103.64,1720.96 2103.92,1720.96 2103.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2103.92 1720.96 L2103.92 1720.96 L2104.21 1720.96 L2104.21 1720.96 L2103.92 1720.96 L2103.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2103.92,1720.96 2103.92,1720.96 2104.21,1720.96 2103.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2104.21 1720.96 L2104.21 1720.96 L2104.49 1720.96 L2104.49 1720.96 L2104.21 1720.96 L2104.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2104.21,1720.96 2104.21,1720.96 2104.49,1720.96 2104.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2104.49 1720.96 L2104.49 1720.96 L2104.77 1720.96 L2104.77 1720.96 L2104.49 1720.96 L2104.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2104.49,1720.96 2104.49,1720.96 2104.77,1720.96 2104.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2104.77 1720.96 L2104.77 1720.96 L2105.05 1720.96 L2105.05 1720.96 L2104.77 1720.96 L2104.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2104.77,1720.96 2104.77,1720.96 2105.05,1720.96 2104.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2105.05 1720.96 L2105.05 1720.96 L2105.33 1720.96 L2105.33 1720.96 L2105.05 1720.96 L2105.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2105.05,1720.96 2105.05,1720.96 2105.33,1720.96 2105.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2105.33 1720.96 L2105.33 1720.96 L2105.61 1720.96 L2105.61 1720.96 L2105.33 1720.96 L2105.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2105.33,1720.96 2105.33,1720.96 2105.61,1720.96 2105.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2105.61 1720.96 L2105.61 1720.96 L2105.9 1720.96 L2105.9 1720.96 L2105.61 1720.96 L2105.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2105.61,1720.96 2105.61,1720.96 2105.9,1720.96 2105.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2105.9 1720.96 L2105.9 1720.96 L2106.18 1720.96 L2106.18 1720.96 L2105.9 1720.96 L2105.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2105.9,1720.96 2105.9,1720.96 2106.18,1720.96 2105.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2106.18 1720.96 L2106.18 1720.96 L2106.46 1720.96 L2106.46 1720.96 L2106.18 1720.96 L2106.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2106.18,1720.96 2106.18,1720.96 2106.46,1720.96 2106.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2106.46 1720.96 L2106.46 1720.96 L2106.74 1720.96 L2106.74 1720.96 L2106.46 1720.96 L2106.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2106.46,1720.96 2106.46,1720.96 2106.74,1720.96 2106.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2106.74 1720.96 L2106.74 1720.96 L2107.02 1720.96 L2107.02 1720.96 L2106.74 1720.96 L2106.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2106.74,1720.96 2106.74,1720.96 2107.02,1720.96 2106.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2107.02 1720.96 L2107.02 1720.96 L2107.31 1720.96 L2107.31 1720.96 L2107.02 1720.96 L2107.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2107.02,1720.96 2107.02,1720.96 2107.31,1720.96 2107.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2107.31 1720.96 L2107.31 1720.96 L2107.59 1720.96 L2107.59 1720.96 L2107.31 1720.96 L2107.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2107.31,1720.96 2107.31,1720.96 2107.59,1720.96 2107.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2107.59 1720.96 L2107.59 1720.96 L2107.87 1720.96 L2107.87 1720.96 L2107.59 1720.96 L2107.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2107.59,1720.96 2107.59,1720.96 2107.87,1720.96 2107.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2107.87 1720.96 L2107.87 1720.96 L2108.15 1720.96 L2108.15 1720.96 L2107.87 1720.96 L2107.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2107.87,1720.96 2107.87,1720.96 2108.15,1720.96 2107.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2108.15 1720.96 L2108.15 1720.96 L2108.43 1720.96 L2108.43 1720.96 L2108.15 1720.96 L2108.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2108.15,1720.96 2108.15,1720.96 2108.43,1720.96 2108.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2108.43 1720.96 L2108.43 1720.96 L2108.71 1720.96 L2108.71 1720.96 L2108.43 1720.96 L2108.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2108.43,1720.96 2108.43,1720.96 2108.71,1720.96 2108.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2108.71 1720.96 L2108.71 1720.96 L2109 1720.96 L2109 1720.96 L2108.71 1720.96 L2108.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2108.71,1720.96 2108.71,1720.96 2109,1720.96 2108.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2109 1720.96 L2109 1720.96 L2109.28 1720.96 L2109.28 1720.96 L2109 1720.96 L2109 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2109,1720.96 2109,1720.96 2109.28,1720.96 2109,1720.96 "/>
<path clip-path="url(#clip322)" d="M2109.28 1720.96 L2109.28 1720.96 L2109.56 1720.96 L2109.56 1720.96 L2109.28 1720.96 L2109.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2109.28,1720.96 2109.28,1720.96 2109.56,1720.96 2109.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2109.56 1720.96 L2109.56 1720.96 L2109.84 1720.96 L2109.84 1720.96 L2109.56 1720.96 L2109.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2109.56,1720.96 2109.56,1720.96 2109.84,1720.96 2109.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2109.84 1720.96 L2109.84 1720.96 L2110.12 1720.96 L2110.12 1720.96 L2109.84 1720.96 L2109.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2109.84,1720.96 2109.84,1720.96 2110.12,1720.96 2109.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2110.12 1720.96 L2110.12 1720.96 L2110.4 1720.96 L2110.4 1720.96 L2110.12 1720.96 L2110.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2110.12,1720.96 2110.12,1720.96 2110.4,1720.96 2110.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2110.4 1720.96 L2110.4 1720.96 L2110.69 1720.96 L2110.69 1720.96 L2110.4 1720.96 L2110.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2110.4,1720.96 2110.4,1720.96 2110.69,1720.96 2110.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2110.69 1720.96 L2110.69 1720.96 L2110.97 1720.96 L2110.97 1720.96 L2110.69 1720.96 L2110.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2110.69,1720.96 2110.69,1720.96 2110.97,1720.96 2110.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2110.97 1720.96 L2110.97 1720.96 L2111.25 1720.96 L2111.25 1720.96 L2110.97 1720.96 L2110.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2110.97,1720.96 2110.97,1720.96 2111.25,1720.96 2110.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2111.25 1720.96 L2111.25 1720.96 L2111.53 1720.96 L2111.53 1720.96 L2111.25 1720.96 L2111.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2111.25,1720.96 2111.25,1720.96 2111.53,1720.96 2111.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2111.53 1720.96 L2111.53 1720.96 L2111.81 1720.96 L2111.81 1720.96 L2111.53 1720.96 L2111.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2111.53,1720.96 2111.53,1720.96 2111.81,1720.96 2111.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2111.81 1720.96 L2111.81 1720.96 L2112.09 1720.96 L2112.09 1720.96 L2111.81 1720.96 L2111.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2111.81,1720.96 2111.81,1720.96 2112.09,1720.96 2111.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2112.09 1720.96 L2112.09 1720.96 L2112.38 1720.96 L2112.38 1720.96 L2112.09 1720.96 L2112.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2112.09,1720.96 2112.09,1720.96 2112.38,1720.96 2112.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2112.38 1720.96 L2112.38 1720.96 L2112.66 1720.96 L2112.66 1720.96 L2112.38 1720.96 L2112.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2112.38,1720.96 2112.38,1720.96 2112.66,1720.96 2112.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2112.66 1720.96 L2112.66 1720.96 L2112.94 1720.96 L2112.94 1720.96 L2112.66 1720.96 L2112.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2112.66,1720.96 2112.66,1720.96 2112.94,1720.96 2112.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2112.94 1720.96 L2112.94 1720.96 L2113.22 1720.96 L2113.22 1720.96 L2112.94 1720.96 L2112.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2112.94,1720.96 2112.94,1720.96 2113.22,1720.96 2112.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2113.22 1720.96 L2113.22 1720.96 L2113.5 1720.96 L2113.5 1720.96 L2113.22 1720.96 L2113.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2113.22,1720.96 2113.22,1720.96 2113.5,1720.96 2113.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2113.5 1720.96 L2113.5 1720.96 L2113.79 1720.96 L2113.79 1720.96 L2113.5 1720.96 L2113.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2113.5,1720.96 2113.5,1720.96 2113.79,1720.96 2113.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2113.79 1720.96 L2113.79 1720.96 L2114.07 1720.96 L2114.07 1720.96 L2113.79 1720.96 L2113.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2113.79,1720.96 2113.79,1720.96 2114.07,1720.96 2113.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2114.07 1720.96 L2114.07 1720.96 L2114.35 1720.96 L2114.35 1720.96 L2114.07 1720.96 L2114.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2114.07,1720.96 2114.07,1720.96 2114.35,1720.96 2114.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2114.35 1720.96 L2114.35 1720.96 L2114.63 1720.96 L2114.63 1720.96 L2114.35 1720.96 L2114.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2114.35,1720.96 2114.35,1720.96 2114.63,1720.96 2114.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2114.63 1720.96 L2114.63 1720.96 L2114.91 1720.96 L2114.91 1720.96 L2114.63 1720.96 L2114.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2114.63,1720.96 2114.63,1720.96 2114.91,1720.96 2114.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2114.91 1720.96 L2114.91 1720.96 L2115.19 1720.96 L2115.19 1720.96 L2114.91 1720.96 L2114.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2114.91,1720.96 2114.91,1720.96 2115.19,1720.96 2114.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2115.19 1720.96 L2115.19 1720.96 L2115.48 1720.96 L2115.48 1720.96 L2115.19 1720.96 L2115.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2115.19,1720.96 2115.19,1720.96 2115.48,1720.96 2115.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2115.48 1720.96 L2115.48 1720.96 L2115.76 1720.96 L2115.76 1720.96 L2115.48 1720.96 L2115.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2115.48,1720.96 2115.48,1720.96 2115.76,1720.96 2115.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2115.76 1720.96 L2115.76 1720.96 L2116.04 1720.96 L2116.04 1720.96 L2115.76 1720.96 L2115.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2115.76,1720.96 2115.76,1720.96 2116.04,1720.96 2115.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2116.04 1720.96 L2116.04 1720.96 L2116.32 1720.96 L2116.32 1720.96 L2116.04 1720.96 L2116.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2116.04,1720.96 2116.04,1720.96 2116.32,1720.96 2116.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2116.32 1720.96 L2116.32 1720.96 L2116.6 1720.96 L2116.6 1720.96 L2116.32 1720.96 L2116.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2116.32,1720.96 2116.32,1720.96 2116.6,1720.96 2116.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2116.6 1720.96 L2116.6 1720.96 L2116.88 1720.96 L2116.88 1720.96 L2116.6 1720.96 L2116.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2116.6,1720.96 2116.6,1720.96 2116.88,1720.96 2116.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2116.88 1720.96 L2116.88 1720.96 L2117.17 1720.96 L2117.17 1720.96 L2116.88 1720.96 L2116.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2116.88,1720.96 2116.88,1720.96 2117.17,1720.96 2116.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2117.17 1720.96 L2117.17 1720.96 L2117.45 1720.96 L2117.45 1720.96 L2117.17 1720.96 L2117.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2117.17,1720.96 2117.17,1720.96 2117.45,1720.96 2117.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2117.45 1720.96 L2117.45 1720.96 L2117.73 1720.96 L2117.73 1720.96 L2117.45 1720.96 L2117.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2117.45,1720.96 2117.45,1720.96 2117.73,1720.96 2117.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2117.73 1720.96 L2117.73 1720.96 L2118.01 1720.96 L2118.01 1720.96 L2117.73 1720.96 L2117.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2117.73,1720.96 2117.73,1720.96 2118.01,1720.96 2117.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2118.01 1720.96 L2118.01 1720.96 L2118.29 1720.96 L2118.29 1720.96 L2118.01 1720.96 L2118.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2118.01,1720.96 2118.01,1720.96 2118.29,1720.96 2118.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2118.29 1720.96 L2118.29 1720.96 L2118.57 1720.96 L2118.57 1720.96 L2118.29 1720.96 L2118.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2118.29,1720.96 2118.29,1720.96 2118.57,1720.96 2118.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2118.57 1720.96 L2118.57 1720.96 L2118.86 1720.96 L2118.86 1720.96 L2118.57 1720.96 L2118.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2118.57,1720.96 2118.57,1720.96 2118.86,1720.96 2118.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2118.86 1720.96 L2118.86 1720.96 L2119.14 1720.96 L2119.14 1720.96 L2118.86 1720.96 L2118.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2118.86,1720.96 2118.86,1720.96 2119.14,1720.96 2118.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2119.14 1720.96 L2119.14 1720.96 L2119.42 1720.96 L2119.42 1720.96 L2119.14 1720.96 L2119.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2119.14,1720.96 2119.14,1720.96 2119.42,1720.96 2119.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2119.42 1720.96 L2119.42 1720.96 L2119.7 1720.96 L2119.7 1720.96 L2119.42 1720.96 L2119.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2119.42,1720.96 2119.42,1720.96 2119.7,1720.96 2119.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2119.7 1720.96 L2119.7 1720.96 L2119.98 1720.96 L2119.98 1720.96 L2119.7 1720.96 L2119.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2119.7,1720.96 2119.7,1720.96 2119.98,1720.96 2119.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2119.98 1720.96 L2119.98 1720.96 L2120.26 1720.96 L2120.26 1720.96 L2119.98 1720.96 L2119.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2119.98,1720.96 2119.98,1720.96 2120.26,1720.96 2119.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2120.26 1720.96 L2120.26 1720.96 L2120.55 1720.96 L2120.55 1720.96 L2120.26 1720.96 L2120.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2120.26,1720.96 2120.26,1720.96 2120.55,1720.96 2120.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2120.55 1720.96 L2120.55 1720.96 L2120.83 1720.96 L2120.83 1720.96 L2120.55 1720.96 L2120.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2120.55,1720.96 2120.55,1720.96 2120.83,1720.96 2120.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2120.83 1720.96 L2120.83 1720.96 L2121.11 1720.96 L2121.11 1720.96 L2120.83 1720.96 L2120.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2120.83,1720.96 2120.83,1720.96 2121.11,1720.96 2120.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2121.11 1720.96 L2121.11 1720.96 L2121.39 1720.96 L2121.39 1720.96 L2121.11 1720.96 L2121.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2121.11,1720.96 2121.11,1720.96 2121.39,1720.96 2121.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2121.39 1720.96 L2121.39 1720.96 L2121.67 1720.96 L2121.67 1720.96 L2121.39 1720.96 L2121.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2121.39,1720.96 2121.39,1720.96 2121.67,1720.96 2121.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2121.67 1720.96 L2121.67 1720.96 L2121.96 1720.96 L2121.96 1720.96 L2121.67 1720.96 L2121.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2121.67,1720.96 2121.67,1720.96 2121.96,1720.96 2121.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2121.96 1720.96 L2121.96 1720.96 L2122.24 1720.96 L2122.24 1720.96 L2121.96 1720.96 L2121.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2121.96,1720.96 2121.96,1720.96 2122.24,1720.96 2121.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2122.24 1720.96 L2122.24 1720.96 L2122.52 1720.96 L2122.52 1720.96 L2122.24 1720.96 L2122.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2122.24,1720.96 2122.24,1720.96 2122.52,1720.96 2122.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2122.52 1720.96 L2122.52 1720.96 L2122.8 1720.96 L2122.8 1720.96 L2122.52 1720.96 L2122.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2122.52,1720.96 2122.52,1720.96 2122.8,1720.96 2122.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2122.8 1720.96 L2122.8 1720.96 L2123.08 1720.96 L2123.08 1720.96 L2122.8 1720.96 L2122.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2122.8,1720.96 2122.8,1720.96 2123.08,1720.96 2122.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2123.08 1720.96 L2123.08 1720.96 L2123.36 1720.96 L2123.36 1720.96 L2123.08 1720.96 L2123.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2123.08,1720.96 2123.08,1720.96 2123.36,1720.96 2123.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2123.36 1720.96 L2123.36 1720.96 L2123.65 1720.96 L2123.65 1720.96 L2123.36 1720.96 L2123.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2123.36,1720.96 2123.36,1720.96 2123.65,1720.96 2123.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2123.65 1720.96 L2123.65 1720.96 L2123.93 1720.96 L2123.93 1720.96 L2123.65 1720.96 L2123.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2123.65,1720.96 2123.65,1720.96 2123.93,1720.96 2123.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2123.93 1720.96 L2123.93 1720.96 L2124.21 1720.96 L2124.21 1720.96 L2123.93 1720.96 L2123.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2123.93,1720.96 2123.93,1720.96 2124.21,1720.96 2123.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2124.21 1720.96 L2124.21 1720.96 L2124.49 1720.96 L2124.49 1720.96 L2124.21 1720.96 L2124.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2124.21,1720.96 2124.21,1720.96 2124.49,1720.96 2124.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2124.49 1720.96 L2124.49 1720.96 L2124.77 1720.96 L2124.77 1720.96 L2124.49 1720.96 L2124.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2124.49,1720.96 2124.49,1720.96 2124.77,1720.96 2124.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2124.77 1720.96 L2124.77 1720.96 L2125.05 1720.96 L2125.05 1720.96 L2124.77 1720.96 L2124.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2124.77,1720.96 2124.77,1720.96 2125.05,1720.96 2124.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2125.05 1720.96 L2125.05 1720.96 L2125.34 1720.96 L2125.34 1720.96 L2125.05 1720.96 L2125.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2125.05,1720.96 2125.05,1720.96 2125.34,1720.96 2125.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2125.34 1720.96 L2125.34 1720.96 L2125.62 1720.96 L2125.62 1720.96 L2125.34 1720.96 L2125.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2125.34,1720.96 2125.34,1720.96 2125.62,1720.96 2125.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2125.62 1720.96 L2125.62 1720.96 L2125.9 1720.96 L2125.9 1720.96 L2125.62 1720.96 L2125.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2125.62,1720.96 2125.62,1720.96 2125.9,1720.96 2125.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2125.9 1720.96 L2125.9 1720.96 L2126.18 1720.96 L2126.18 1720.96 L2125.9 1720.96 L2125.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2125.9,1720.96 2125.9,1720.96 2126.18,1720.96 2125.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2126.18 1720.96 L2126.18 1720.96 L2126.46 1720.96 L2126.46 1720.96 L2126.18 1720.96 L2126.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2126.18,1720.96 2126.18,1720.96 2126.46,1720.96 2126.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2126.46 1720.96 L2126.46 1720.96 L2126.74 1720.96 L2126.74 1720.96 L2126.46 1720.96 L2126.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2126.46,1720.96 2126.46,1720.96 2126.74,1720.96 2126.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2126.74 1720.96 L2126.74 1720.96 L2127.03 1720.96 L2127.03 1720.96 L2126.74 1720.96 L2126.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2126.74,1720.96 2126.74,1720.96 2127.03,1720.96 2126.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2127.03 1720.96 L2127.03 1720.96 L2127.31 1720.96 L2127.31 1720.96 L2127.03 1720.96 L2127.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2127.03,1720.96 2127.03,1720.96 2127.31,1720.96 2127.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2127.31 1720.96 L2127.31 1720.96 L2127.59 1720.96 L2127.59 1720.96 L2127.31 1720.96 L2127.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2127.31,1720.96 2127.31,1720.96 2127.59,1720.96 2127.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2127.59 1720.96 L2127.59 1720.96 L2127.87 1720.96 L2127.87 1720.96 L2127.59 1720.96 L2127.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2127.59,1720.96 2127.59,1720.96 2127.87,1720.96 2127.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2127.87 1720.96 L2127.87 1720.96 L2128.15 1720.96 L2128.15 1720.96 L2127.87 1720.96 L2127.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2127.87,1720.96 2127.87,1720.96 2128.15,1720.96 2127.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2128.15 1720.96 L2128.15 1720.96 L2128.43 1720.96 L2128.43 1720.96 L2128.15 1720.96 L2128.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2128.15,1720.96 2128.15,1720.96 2128.43,1720.96 2128.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2128.43 1720.96 L2128.43 1720.96 L2128.72 1720.96 L2128.72 1720.96 L2128.43 1720.96 L2128.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2128.43,1720.96 2128.43,1720.96 2128.72,1720.96 2128.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2128.72 1720.96 L2128.72 1720.96 L2129 1720.96 L2129 1720.96 L2128.72 1720.96 L2128.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2128.72,1720.96 2128.72,1720.96 2129,1720.96 2128.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2129 1720.96 L2129 1720.96 L2129.28 1720.96 L2129.28 1720.96 L2129 1720.96 L2129 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2129,1720.96 2129,1720.96 2129.28,1720.96 2129,1720.96 "/>
<path clip-path="url(#clip322)" d="M2129.28 1720.96 L2129.28 1720.96 L2129.56 1720.96 L2129.56 1720.96 L2129.28 1720.96 L2129.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2129.28,1720.96 2129.28,1720.96 2129.56,1720.96 2129.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2129.56 1720.96 L2129.56 1720.96 L2129.84 1720.96 L2129.84 1720.96 L2129.56 1720.96 L2129.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2129.56,1720.96 2129.56,1720.96 2129.84,1720.96 2129.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2129.84 1720.96 L2129.84 1720.96 L2130.13 1720.96 L2130.13 1720.96 L2129.84 1720.96 L2129.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2129.84,1720.96 2129.84,1720.96 2130.13,1720.96 2129.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2130.13 1720.96 L2130.13 1720.96 L2130.41 1720.96 L2130.41 1720.96 L2130.13 1720.96 L2130.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2130.13,1720.96 2130.13,1720.96 2130.41,1720.96 2130.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2130.41 1720.96 L2130.41 1720.96 L2130.69 1720.96 L2130.69 1720.96 L2130.41 1720.96 L2130.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2130.41,1720.96 2130.41,1720.96 2130.69,1720.96 2130.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2130.69 1720.96 L2130.69 1720.96 L2130.97 1720.96 L2130.97 1720.96 L2130.69 1720.96 L2130.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2130.69,1720.96 2130.69,1720.96 2130.97,1720.96 2130.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2130.97 1720.96 L2130.97 1720.96 L2131.25 1720.96 L2131.25 1720.96 L2130.97 1720.96 L2130.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2130.97,1720.96 2130.97,1720.96 2131.25,1720.96 2130.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2131.25 1720.96 L2131.25 1720.96 L2131.53 1720.96 L2131.53 1720.96 L2131.25 1720.96 L2131.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2131.25,1720.96 2131.25,1720.96 2131.53,1720.96 2131.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2131.53 1720.96 L2131.53 1720.96 L2131.82 1720.96 L2131.82 1720.96 L2131.53 1720.96 L2131.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2131.53,1720.96 2131.53,1720.96 2131.82,1720.96 2131.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2131.82 1720.96 L2131.82 1720.96 L2132.1 1720.96 L2132.1 1720.96 L2131.82 1720.96 L2131.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2131.82,1720.96 2131.82,1720.96 2132.1,1720.96 2131.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2132.1 1720.96 L2132.1 1720.96 L2132.38 1720.96 L2132.38 1720.96 L2132.1 1720.96 L2132.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2132.1,1720.96 2132.1,1720.96 2132.38,1720.96 2132.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2132.38 1720.96 L2132.38 1720.96 L2132.66 1720.96 L2132.66 1720.96 L2132.38 1720.96 L2132.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2132.38,1720.96 2132.38,1720.96 2132.66,1720.96 2132.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2132.66 1720.96 L2132.66 1720.96 L2132.94 1720.96 L2132.94 1720.96 L2132.66 1720.96 L2132.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2132.66,1720.96 2132.66,1720.96 2132.94,1720.96 2132.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2132.94 1720.96 L2132.94 1720.96 L2133.22 1720.96 L2133.22 1720.96 L2132.94 1720.96 L2132.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2132.94,1720.96 2132.94,1720.96 2133.22,1720.96 2132.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2133.22 1720.96 L2133.22 1720.96 L2133.51 1720.96 L2133.51 1720.96 L2133.22 1720.96 L2133.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2133.22,1720.96 2133.22,1720.96 2133.51,1720.96 2133.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2133.51 1720.96 L2133.51 1720.96 L2133.79 1720.96 L2133.79 1720.96 L2133.51 1720.96 L2133.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2133.51,1720.96 2133.51,1720.96 2133.79,1720.96 2133.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2133.79 1720.96 L2133.79 1720.96 L2134.07 1720.96 L2134.07 1720.96 L2133.79 1720.96 L2133.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2133.79,1720.96 2133.79,1720.96 2134.07,1720.96 2133.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2134.07 1720.96 L2134.07 1720.96 L2134.35 1720.96 L2134.35 1720.96 L2134.07 1720.96 L2134.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2134.07,1720.96 2134.07,1720.96 2134.35,1720.96 2134.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2134.35 1720.96 L2134.35 1720.96 L2134.63 1720.96 L2134.63 1720.96 L2134.35 1720.96 L2134.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2134.35,1720.96 2134.35,1720.96 2134.63,1720.96 2134.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2134.63 1720.96 L2134.63 1720.96 L2134.91 1720.96 L2134.91 1720.96 L2134.63 1720.96 L2134.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2134.63,1720.96 2134.63,1720.96 2134.91,1720.96 2134.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2134.91 1720.96 L2134.91 1720.96 L2135.2 1720.96 L2135.2 1720.96 L2134.91 1720.96 L2134.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2134.91,1720.96 2134.91,1720.96 2135.2,1720.96 2134.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2135.2 1720.96 L2135.2 1720.96 L2135.48 1720.96 L2135.48 1720.96 L2135.2 1720.96 L2135.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2135.2,1720.96 2135.2,1720.96 2135.48,1720.96 2135.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2135.48 1720.96 L2135.48 1720.96 L2135.76 1720.96 L2135.76 1720.96 L2135.48 1720.96 L2135.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2135.48,1720.96 2135.48,1720.96 2135.76,1720.96 2135.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2135.76 1720.96 L2135.76 1720.96 L2136.04 1720.96 L2136.04 1720.96 L2135.76 1720.96 L2135.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2135.76,1720.96 2135.76,1720.96 2136.04,1720.96 2135.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2136.04 1720.96 L2136.04 1720.96 L2136.32 1720.96 L2136.32 1720.96 L2136.04 1720.96 L2136.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2136.04,1720.96 2136.04,1720.96 2136.32,1720.96 2136.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2136.32 1720.96 L2136.32 1720.96 L2136.6 1720.96 L2136.6 1720.96 L2136.32 1720.96 L2136.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2136.32,1720.96 2136.32,1720.96 2136.6,1720.96 2136.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2136.6 1720.96 L2136.6 1720.96 L2136.89 1720.96 L2136.89 1720.96 L2136.6 1720.96 L2136.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2136.6,1720.96 2136.6,1720.96 2136.89,1720.96 2136.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2136.89 1720.96 L2136.89 1720.96 L2137.17 1720.96 L2137.17 1720.96 L2136.89 1720.96 L2136.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2136.89,1720.96 2136.89,1720.96 2137.17,1720.96 2136.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2137.17 1720.96 L2137.17 1720.96 L2137.45 1720.96 L2137.45 1720.96 L2137.17 1720.96 L2137.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2137.17,1720.96 2137.17,1720.96 2137.45,1720.96 2137.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2137.45 1720.96 L2137.45 1720.96 L2137.73 1720.96 L2137.73 1720.96 L2137.45 1720.96 L2137.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2137.45,1720.96 2137.45,1720.96 2137.73,1720.96 2137.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2137.73 1720.96 L2137.73 1720.96 L2138.01 1720.96 L2138.01 1720.96 L2137.73 1720.96 L2137.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2137.73,1720.96 2137.73,1720.96 2138.01,1720.96 2137.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2138.01 1720.96 L2138.01 1720.96 L2138.3 1720.96 L2138.3 1720.96 L2138.01 1720.96 L2138.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2138.01,1720.96 2138.01,1720.96 2138.3,1720.96 2138.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2138.3 1720.96 L2138.3 1720.96 L2138.58 1720.96 L2138.58 1720.96 L2138.3 1720.96 L2138.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2138.3,1720.96 2138.3,1720.96 2138.58,1720.96 2138.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2138.58 1720.96 L2138.58 1720.96 L2138.86 1720.96 L2138.86 1720.96 L2138.58 1720.96 L2138.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2138.58,1720.96 2138.58,1720.96 2138.86,1720.96 2138.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2138.86 1720.96 L2138.86 1720.96 L2139.14 1720.96 L2139.14 1720.96 L2138.86 1720.96 L2138.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2138.86,1720.96 2138.86,1720.96 2139.14,1720.96 2138.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2139.14 1720.96 L2139.14 1720.96 L2139.42 1720.96 L2139.42 1720.96 L2139.14 1720.96 L2139.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2139.14,1720.96 2139.14,1720.96 2139.42,1720.96 2139.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2139.42 1720.96 L2139.42 1720.96 L2139.7 1720.96 L2139.7 1720.96 L2139.42 1720.96 L2139.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2139.42,1720.96 2139.42,1720.96 2139.7,1720.96 2139.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2139.7 1720.96 L2139.7 1720.96 L2139.99 1720.96 L2139.99 1720.96 L2139.7 1720.96 L2139.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2139.7,1720.96 2139.7,1720.96 2139.99,1720.96 2139.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2139.99 1720.96 L2139.99 1720.96 L2140.27 1720.96 L2140.27 1720.96 L2139.99 1720.96 L2139.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2139.99,1720.96 2139.99,1720.96 2140.27,1720.96 2139.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2140.27 1720.96 L2140.27 1720.96 L2140.55 1720.96 L2140.55 1720.96 L2140.27 1720.96 L2140.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2140.27,1720.96 2140.27,1720.96 2140.55,1720.96 2140.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2140.55 1720.96 L2140.55 1720.96 L2140.83 1720.96 L2140.83 1720.96 L2140.55 1720.96 L2140.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2140.55,1720.96 2140.55,1720.96 2140.83,1720.96 2140.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2140.83 1720.96 L2140.83 1720.96 L2141.11 1720.96 L2141.11 1720.96 L2140.83 1720.96 L2140.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2140.83,1720.96 2140.83,1720.96 2141.11,1720.96 2140.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2141.11 1720.96 L2141.11 1720.96 L2141.39 1720.96 L2141.39 1720.96 L2141.11 1720.96 L2141.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2141.11,1720.96 2141.11,1720.96 2141.39,1720.96 2141.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2141.39 1720.96 L2141.39 1720.96 L2141.68 1720.96 L2141.68 1720.96 L2141.39 1720.96 L2141.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2141.39,1720.96 2141.39,1720.96 2141.68,1720.96 2141.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2141.68 1720.96 L2141.68 1720.96 L2141.96 1720.96 L2141.96 1720.96 L2141.68 1720.96 L2141.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2141.68,1720.96 2141.68,1720.96 2141.96,1720.96 2141.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2141.96 1720.96 L2141.96 1720.96 L2142.24 1720.96 L2142.24 1720.96 L2141.96 1720.96 L2141.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2141.96,1720.96 2141.96,1720.96 2142.24,1720.96 2141.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2142.24 1720.96 L2142.24 1720.96 L2142.52 1720.96 L2142.52 1720.96 L2142.24 1720.96 L2142.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2142.24,1720.96 2142.24,1720.96 2142.52,1720.96 2142.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2142.52 1720.96 L2142.52 1720.96 L2142.8 1720.96 L2142.8 1720.96 L2142.52 1720.96 L2142.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2142.52,1720.96 2142.52,1720.96 2142.8,1720.96 2142.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2142.8 1720.96 L2142.8 1720.96 L2143.08 1720.96 L2143.08 1720.96 L2142.8 1720.96 L2142.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2142.8,1720.96 2142.8,1720.96 2143.08,1720.96 2142.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2143.08 1720.96 L2143.08 1720.96 L2143.37 1720.96 L2143.37 1720.96 L2143.08 1720.96 L2143.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2143.08,1720.96 2143.08,1720.96 2143.37,1720.96 2143.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2143.37 1720.96 L2143.37 1720.96 L2143.65 1720.96 L2143.65 1720.96 L2143.37 1720.96 L2143.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2143.37,1720.96 2143.37,1720.96 2143.65,1720.96 2143.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2143.65 1720.96 L2143.65 1720.96 L2143.93 1720.96 L2143.93 1720.96 L2143.65 1720.96 L2143.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2143.65,1720.96 2143.65,1720.96 2143.93,1720.96 2143.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2143.93 1720.96 L2143.93 1720.96 L2144.21 1720.96 L2144.21 1720.96 L2143.93 1720.96 L2143.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2143.93,1720.96 2143.93,1720.96 2144.21,1720.96 2143.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2144.21 1720.96 L2144.21 1720.96 L2144.49 1720.96 L2144.49 1720.96 L2144.21 1720.96 L2144.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2144.21,1720.96 2144.21,1720.96 2144.49,1720.96 2144.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2144.49 1720.96 L2144.49 1720.96 L2144.77 1720.96 L2144.77 1720.96 L2144.49 1720.96 L2144.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2144.49,1720.96 2144.49,1720.96 2144.77,1720.96 2144.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2144.77 1720.96 L2144.77 1720.96 L2145.06 1720.96 L2145.06 1720.96 L2144.77 1720.96 L2144.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2144.77,1720.96 2144.77,1720.96 2145.06,1720.96 2144.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2145.06 1720.96 L2145.06 1720.96 L2145.34 1720.96 L2145.34 1720.96 L2145.06 1720.96 L2145.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2145.06,1720.96 2145.06,1720.96 2145.34,1720.96 2145.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2145.34 1720.96 L2145.34 1720.96 L2145.62 1720.96 L2145.62 1720.96 L2145.34 1720.96 L2145.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2145.34,1720.96 2145.34,1720.96 2145.62,1720.96 2145.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2145.62 1720.96 L2145.62 1720.96 L2145.9 1720.96 L2145.9 1720.96 L2145.62 1720.96 L2145.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2145.62,1720.96 2145.62,1720.96 2145.9,1720.96 2145.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2145.9 1720.96 L2145.9 1720.96 L2146.18 1720.96 L2146.18 1720.96 L2145.9 1720.96 L2145.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2145.9,1720.96 2145.9,1720.96 2146.18,1720.96 2145.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2146.18 1720.96 L2146.18 1720.96 L2146.47 1720.96 L2146.47 1720.96 L2146.18 1720.96 L2146.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2146.18,1720.96 2146.18,1720.96 2146.47,1720.96 2146.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2146.47 1720.96 L2146.47 1720.96 L2146.75 1720.96 L2146.75 1720.96 L2146.47 1720.96 L2146.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2146.47,1720.96 2146.47,1720.96 2146.75,1720.96 2146.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2146.75 1720.96 L2146.75 1720.96 L2147.03 1720.96 L2147.03 1720.96 L2146.75 1720.96 L2146.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2146.75,1720.96 2146.75,1720.96 2147.03,1720.96 2146.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2147.03 1720.96 L2147.03 1720.96 L2147.31 1720.96 L2147.31 1720.96 L2147.03 1720.96 L2147.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2147.03,1720.96 2147.03,1720.96 2147.31,1720.96 2147.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2147.31 1720.96 L2147.31 1720.96 L2147.59 1720.96 L2147.59 1720.96 L2147.31 1720.96 L2147.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2147.31,1720.96 2147.31,1720.96 2147.59,1720.96 2147.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2147.59 1720.96 L2147.59 1720.96 L2147.87 1720.96 L2147.87 1720.96 L2147.59 1720.96 L2147.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2147.59,1720.96 2147.59,1720.96 2147.87,1720.96 2147.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2147.87 1720.96 L2147.87 1720.96 L2148.16 1720.96 L2148.16 1720.96 L2147.87 1720.96 L2147.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2147.87,1720.96 2147.87,1720.96 2148.16,1720.96 2147.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2148.16 1720.96 L2148.16 1720.96 L2148.44 1720.96 L2148.44 1720.96 L2148.16 1720.96 L2148.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2148.16,1720.96 2148.16,1720.96 2148.44,1720.96 2148.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2148.44 1720.96 L2148.44 1720.96 L2148.72 1720.96 L2148.72 1720.96 L2148.44 1720.96 L2148.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2148.44,1720.96 2148.44,1720.96 2148.72,1720.96 2148.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2148.72 1720.96 L2148.72 1720.96 L2149 1720.96 L2149 1720.96 L2148.72 1720.96 L2148.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2148.72,1720.96 2148.72,1720.96 2149,1720.96 2148.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2149 1720.96 L2149 1720.96 L2149.28 1720.96 L2149.28 1720.96 L2149 1720.96 L2149 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2149,1720.96 2149,1720.96 2149.28,1720.96 2149,1720.96 "/>
<path clip-path="url(#clip322)" d="M2149.28 1720.96 L2149.28 1720.96 L2149.56 1720.96 L2149.56 1720.96 L2149.28 1720.96 L2149.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2149.28,1720.96 2149.28,1720.96 2149.56,1720.96 2149.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2149.56 1720.96 L2149.56 1720.96 L2149.85 1720.96 L2149.85 1720.96 L2149.56 1720.96 L2149.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2149.56,1720.96 2149.56,1720.96 2149.85,1720.96 2149.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2149.85 1720.96 L2149.85 1720.96 L2150.13 1720.96 L2150.13 1720.96 L2149.85 1720.96 L2149.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2149.85,1720.96 2149.85,1720.96 2150.13,1720.96 2149.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2150.13 1720.96 L2150.13 1720.96 L2150.41 1720.96 L2150.41 1720.96 L2150.13 1720.96 L2150.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2150.13,1720.96 2150.13,1720.96 2150.41,1720.96 2150.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2150.41 1720.96 L2150.41 1720.96 L2150.69 1720.96 L2150.69 1720.96 L2150.41 1720.96 L2150.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2150.41,1720.96 2150.41,1720.96 2150.69,1720.96 2150.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2150.69 1720.96 L2150.69 1720.96 L2150.97 1720.96 L2150.97 1720.96 L2150.69 1720.96 L2150.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2150.69,1720.96 2150.69,1720.96 2150.97,1720.96 2150.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2150.97 1720.96 L2150.97 1720.96 L2151.25 1720.96 L2151.25 1720.96 L2150.97 1720.96 L2150.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2150.97,1720.96 2150.97,1720.96 2151.25,1720.96 2150.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2151.25 1720.96 L2151.25 1720.96 L2151.54 1720.96 L2151.54 1720.96 L2151.25 1720.96 L2151.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2151.25,1720.96 2151.25,1720.96 2151.54,1720.96 2151.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2151.54 1720.96 L2151.54 1720.96 L2151.82 1720.96 L2151.82 1720.96 L2151.54 1720.96 L2151.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2151.54,1720.96 2151.54,1720.96 2151.82,1720.96 2151.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2151.82 1720.96 L2151.82 1720.96 L2152.1 1720.96 L2152.1 1720.96 L2151.82 1720.96 L2151.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2151.82,1720.96 2151.82,1720.96 2152.1,1720.96 2151.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2152.1 1720.96 L2152.1 1720.96 L2152.38 1720.96 L2152.38 1720.96 L2152.1 1720.96 L2152.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2152.1,1720.96 2152.1,1720.96 2152.38,1720.96 2152.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2152.38 1720.96 L2152.38 1720.96 L2152.66 1720.96 L2152.66 1720.96 L2152.38 1720.96 L2152.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2152.38,1720.96 2152.38,1720.96 2152.66,1720.96 2152.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2152.66 1720.96 L2152.66 1720.96 L2152.94 1720.96 L2152.94 1720.96 L2152.66 1720.96 L2152.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2152.66,1720.96 2152.66,1720.96 2152.94,1720.96 2152.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2152.94 1720.96 L2152.94 1720.96 L2153.23 1720.96 L2153.23 1720.96 L2152.94 1720.96 L2152.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2152.94,1720.96 2152.94,1720.96 2153.23,1720.96 2152.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2153.23 1720.96 L2153.23 1720.96 L2153.51 1720.96 L2153.51 1720.96 L2153.23 1720.96 L2153.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2153.23,1720.96 2153.23,1720.96 2153.51,1720.96 2153.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2153.51 1720.96 L2153.51 1720.96 L2153.79 1720.96 L2153.79 1720.96 L2153.51 1720.96 L2153.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2153.51,1720.96 2153.51,1720.96 2153.79,1720.96 2153.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2153.79 1720.96 L2153.79 1720.96 L2154.07 1720.96 L2154.07 1720.96 L2153.79 1720.96 L2153.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2153.79,1720.96 2153.79,1720.96 2154.07,1720.96 2153.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2154.07 1720.96 L2154.07 1720.96 L2154.35 1720.96 L2154.35 1720.96 L2154.07 1720.96 L2154.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2154.07,1720.96 2154.07,1720.96 2154.35,1720.96 2154.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2154.35 1720.96 L2154.35 1720.96 L2154.64 1720.96 L2154.64 1720.96 L2154.35 1720.96 L2154.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2154.35,1720.96 2154.35,1720.96 2154.64,1720.96 2154.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2154.64 1720.96 L2154.64 1720.96 L2154.92 1720.96 L2154.92 1720.96 L2154.64 1720.96 L2154.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2154.64,1720.96 2154.64,1720.96 2154.92,1720.96 2154.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2154.92 1720.96 L2154.92 1720.96 L2155.2 1720.96 L2155.2 1720.96 L2154.92 1720.96 L2154.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2154.92,1720.96 2154.92,1720.96 2155.2,1720.96 2154.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2155.2 1720.96 L2155.2 1720.96 L2155.48 1720.96 L2155.48 1720.96 L2155.2 1720.96 L2155.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2155.2,1720.96 2155.2,1720.96 2155.48,1720.96 2155.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2155.48 1720.96 L2155.48 1720.96 L2155.76 1720.96 L2155.76 1720.96 L2155.48 1720.96 L2155.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2155.48,1720.96 2155.48,1720.96 2155.76,1720.96 2155.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2155.76 1720.96 L2155.76 1720.96 L2156.04 1720.96 L2156.04 1720.96 L2155.76 1720.96 L2155.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2155.76,1720.96 2155.76,1720.96 2156.04,1720.96 2155.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2156.04 1720.96 L2156.04 1720.96 L2156.33 1720.96 L2156.33 1720.96 L2156.04 1720.96 L2156.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2156.04,1720.96 2156.04,1720.96 2156.33,1720.96 2156.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2156.33 1720.96 L2156.33 1720.96 L2156.61 1720.96 L2156.61 1720.96 L2156.33 1720.96 L2156.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2156.33,1720.96 2156.33,1720.96 2156.61,1720.96 2156.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2156.61 1720.96 L2156.61 1720.96 L2156.89 1720.96 L2156.89 1720.96 L2156.61 1720.96 L2156.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2156.61,1720.96 2156.61,1720.96 2156.89,1720.96 2156.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2156.89 1720.96 L2156.89 1720.96 L2157.17 1720.96 L2157.17 1720.96 L2156.89 1720.96 L2156.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2156.89,1720.96 2156.89,1720.96 2157.17,1720.96 2156.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2157.17 1720.96 L2157.17 1720.96 L2157.45 1720.96 L2157.45 1720.96 L2157.17 1720.96 L2157.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2157.17,1720.96 2157.17,1720.96 2157.45,1720.96 2157.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2157.45 1720.96 L2157.45 1720.96 L2157.73 1720.96 L2157.73 1720.96 L2157.45 1720.96 L2157.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2157.45,1720.96 2157.45,1720.96 2157.73,1720.96 2157.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2157.73 1720.96 L2157.73 1720.96 L2158.02 1720.96 L2158.02 1720.96 L2157.73 1720.96 L2157.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2157.73,1720.96 2157.73,1720.96 2158.02,1720.96 2157.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2158.02 1720.96 L2158.02 1720.96 L2158.3 1720.96 L2158.3 1720.96 L2158.02 1720.96 L2158.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2158.02,1720.96 2158.02,1720.96 2158.3,1720.96 2158.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2158.3 1720.96 L2158.3 1720.96 L2158.58 1720.96 L2158.58 1720.96 L2158.3 1720.96 L2158.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2158.3,1720.96 2158.3,1720.96 2158.58,1720.96 2158.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2158.58 1720.96 L2158.58 1720.96 L2158.86 1720.96 L2158.86 1720.96 L2158.58 1720.96 L2158.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2158.58,1720.96 2158.58,1720.96 2158.86,1720.96 2158.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2158.86 1720.96 L2158.86 1720.96 L2159.14 1720.96 L2159.14 1720.96 L2158.86 1720.96 L2158.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2158.86,1720.96 2158.86,1720.96 2159.14,1720.96 2158.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2159.14 1720.96 L2159.14 1720.96 L2159.42 1720.96 L2159.42 1720.96 L2159.14 1720.96 L2159.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2159.14,1720.96 2159.14,1720.96 2159.42,1720.96 2159.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2159.42 1720.96 L2159.42 1720.96 L2159.71 1720.96 L2159.71 1720.96 L2159.42 1720.96 L2159.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2159.42,1720.96 2159.42,1720.96 2159.71,1720.96 2159.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2159.71 1720.96 L2159.71 1720.96 L2159.99 1720.96 L2159.99 1720.96 L2159.71 1720.96 L2159.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2159.71,1720.96 2159.71,1720.96 2159.99,1720.96 2159.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2159.99 1720.96 L2159.99 1720.96 L2160.27 1720.96 L2160.27 1720.96 L2159.99 1720.96 L2159.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2159.99,1720.96 2159.99,1720.96 2160.27,1720.96 2159.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2160.27 1720.96 L2160.27 1720.96 L2160.55 1720.96 L2160.55 1720.96 L2160.27 1720.96 L2160.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2160.27,1720.96 2160.27,1720.96 2160.55,1720.96 2160.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2160.55 1720.96 L2160.55 1720.96 L2160.83 1720.96 L2160.83 1720.96 L2160.55 1720.96 L2160.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2160.55,1720.96 2160.55,1720.96 2160.83,1720.96 2160.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2160.83 1720.96 L2160.83 1720.96 L2161.11 1720.96 L2161.11 1720.96 L2160.83 1720.96 L2160.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2160.83,1720.96 2160.83,1720.96 2161.11,1720.96 2160.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2161.11 1720.96 L2161.11 1720.96 L2161.4 1720.96 L2161.4 1720.96 L2161.11 1720.96 L2161.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2161.11,1720.96 2161.11,1720.96 2161.4,1720.96 2161.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2161.4 1720.96 L2161.4 1720.96 L2161.68 1720.96 L2161.68 1720.96 L2161.4 1720.96 L2161.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2161.4,1720.96 2161.4,1720.96 2161.68,1720.96 2161.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2161.68 1720.96 L2161.68 1720.96 L2161.96 1720.96 L2161.96 1720.96 L2161.68 1720.96 L2161.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2161.68,1720.96 2161.68,1720.96 2161.96,1720.96 2161.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2161.96 1720.96 L2161.96 1720.96 L2162.24 1720.96 L2162.24 1720.96 L2161.96 1720.96 L2161.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2161.96,1720.96 2161.96,1720.96 2162.24,1720.96 2161.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2162.24 1720.96 L2162.24 1720.96 L2162.52 1720.96 L2162.52 1720.96 L2162.24 1720.96 L2162.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2162.24,1720.96 2162.24,1720.96 2162.52,1720.96 2162.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2162.52 1720.96 L2162.52 1720.96 L2162.81 1720.96 L2162.81 1720.96 L2162.52 1720.96 L2162.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2162.52,1720.96 2162.52,1720.96 2162.81,1720.96 2162.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2162.81 1720.96 L2162.81 1720.96 L2163.09 1720.96 L2163.09 1720.96 L2162.81 1720.96 L2162.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2162.81,1720.96 2162.81,1720.96 2163.09,1720.96 2162.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2163.09 1720.96 L2163.09 1720.96 L2163.37 1720.96 L2163.37 1720.96 L2163.09 1720.96 L2163.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2163.09,1720.96 2163.09,1720.96 2163.37,1720.96 2163.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2163.37 1720.96 L2163.37 1720.96 L2163.65 1720.96 L2163.65 1720.96 L2163.37 1720.96 L2163.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2163.37,1720.96 2163.37,1720.96 2163.65,1720.96 2163.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2163.65 1720.96 L2163.65 1720.96 L2163.93 1720.96 L2163.93 1720.96 L2163.65 1720.96 L2163.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2163.65,1720.96 2163.65,1720.96 2163.93,1720.96 2163.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2163.93 1720.96 L2163.93 1720.96 L2164.21 1720.96 L2164.21 1720.96 L2163.93 1720.96 L2163.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2163.93,1720.96 2163.93,1720.96 2164.21,1720.96 2163.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2164.21 1720.96 L2164.21 1720.96 L2164.5 1720.96 L2164.5 1720.96 L2164.21 1720.96 L2164.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2164.21,1720.96 2164.21,1720.96 2164.5,1720.96 2164.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2164.5 1720.96 L2164.5 1720.96 L2164.78 1720.96 L2164.78 1720.96 L2164.5 1720.96 L2164.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2164.5,1720.96 2164.5,1720.96 2164.78,1720.96 2164.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2164.78 1720.96 L2164.78 1720.96 L2165.06 1720.96 L2165.06 1720.96 L2164.78 1720.96 L2164.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2164.78,1720.96 2164.78,1720.96 2165.06,1720.96 2164.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2165.06 1720.96 L2165.06 1720.96 L2165.34 1720.96 L2165.34 1720.96 L2165.06 1720.96 L2165.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2165.06,1720.96 2165.06,1720.96 2165.34,1720.96 2165.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2165.34 1720.96 L2165.34 1720.96 L2165.62 1720.96 L2165.62 1720.96 L2165.34 1720.96 L2165.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2165.34,1720.96 2165.34,1720.96 2165.62,1720.96 2165.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2165.62 1720.96 L2165.62 1720.96 L2165.9 1720.96 L2165.9 1720.96 L2165.62 1720.96 L2165.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2165.62,1720.96 2165.62,1720.96 2165.9,1720.96 2165.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2165.9 1720.96 L2165.9 1720.96 L2166.19 1720.96 L2166.19 1720.96 L2165.9 1720.96 L2165.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2165.9,1720.96 2165.9,1720.96 2166.19,1720.96 2165.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2166.19 1720.96 L2166.19 1720.96 L2166.47 1720.96 L2166.47 1720.96 L2166.19 1720.96 L2166.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2166.19,1720.96 2166.19,1720.96 2166.47,1720.96 2166.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2166.47 1720.96 L2166.47 1720.96 L2166.75 1720.96 L2166.75 1720.96 L2166.47 1720.96 L2166.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2166.47,1720.96 2166.47,1720.96 2166.75,1720.96 2166.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2166.75 1720.96 L2166.75 1720.96 L2167.03 1720.96 L2167.03 1720.96 L2166.75 1720.96 L2166.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2166.75,1720.96 2166.75,1720.96 2167.03,1720.96 2166.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2167.03 1720.96 L2167.03 1720.96 L2167.31 1720.96 L2167.31 1720.96 L2167.03 1720.96 L2167.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2167.03,1720.96 2167.03,1720.96 2167.31,1720.96 2167.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2167.31 1720.96 L2167.31 1720.96 L2167.59 1720.96 L2167.59 1720.96 L2167.31 1720.96 L2167.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2167.31,1720.96 2167.31,1720.96 2167.59,1720.96 2167.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2167.59 1720.96 L2167.59 1720.96 L2167.88 1720.96 L2167.88 1720.96 L2167.59 1720.96 L2167.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2167.59,1720.96 2167.59,1720.96 2167.88,1720.96 2167.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2167.88 1720.96 L2167.88 1720.96 L2168.16 1720.96 L2168.16 1720.96 L2167.88 1720.96 L2167.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2167.88,1720.96 2167.88,1720.96 2168.16,1720.96 2167.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2168.16 1720.96 L2168.16 1720.96 L2168.44 1720.96 L2168.44 1720.96 L2168.16 1720.96 L2168.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2168.16,1720.96 2168.16,1720.96 2168.44,1720.96 2168.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2168.44 1720.96 L2168.44 1720.96 L2168.72 1720.96 L2168.72 1720.96 L2168.44 1720.96 L2168.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2168.44,1720.96 2168.44,1720.96 2168.72,1720.96 2168.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2168.72 1720.96 L2168.72 1720.96 L2169 1720.96 L2169 1720.96 L2168.72 1720.96 L2168.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2168.72,1720.96 2168.72,1720.96 2169,1720.96 2168.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2169 1720.96 L2169 1720.96 L2169.28 1720.96 L2169.28 1720.96 L2169 1720.96 L2169 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2169,1720.96 2169,1720.96 2169.28,1720.96 2169,1720.96 "/>
<path clip-path="url(#clip322)" d="M2169.28 1720.96 L2169.28 1720.96 L2169.57 1720.96 L2169.57 1720.96 L2169.28 1720.96 L2169.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2169.28,1720.96 2169.28,1720.96 2169.57,1720.96 2169.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2169.57 1720.96 L2169.57 1720.96 L2169.85 1720.96 L2169.85 1720.96 L2169.57 1720.96 L2169.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2169.57,1720.96 2169.57,1720.96 2169.85,1720.96 2169.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2169.85 1720.96 L2169.85 1720.96 L2170.13 1720.96 L2170.13 1720.96 L2169.85 1720.96 L2169.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2169.85,1720.96 2169.85,1720.96 2170.13,1720.96 2169.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2170.13 1720.96 L2170.13 1720.96 L2170.41 1720.96 L2170.41 1720.96 L2170.13 1720.96 L2170.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2170.13,1720.96 2170.13,1720.96 2170.41,1720.96 2170.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2170.41 1720.96 L2170.41 1720.96 L2170.69 1720.96 L2170.69 1720.96 L2170.41 1720.96 L2170.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2170.41,1720.96 2170.41,1720.96 2170.69,1720.96 2170.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2170.69 1720.96 L2170.69 1720.96 L2170.98 1720.96 L2170.98 1720.96 L2170.69 1720.96 L2170.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2170.69,1720.96 2170.69,1720.96 2170.98,1720.96 2170.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2170.98 1720.96 L2170.98 1720.96 L2171.26 1720.96 L2171.26 1720.96 L2170.98 1720.96 L2170.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2170.98,1720.96 2170.98,1720.96 2171.26,1720.96 2170.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2171.26 1720.96 L2171.26 1720.96 L2171.54 1720.96 L2171.54 1720.96 L2171.26 1720.96 L2171.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2171.26,1720.96 2171.26,1720.96 2171.54,1720.96 2171.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2171.54 1720.96 L2171.54 1720.96 L2171.82 1720.96 L2171.82 1720.96 L2171.54 1720.96 L2171.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2171.54,1720.96 2171.54,1720.96 2171.82,1720.96 2171.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2171.82 1720.96 L2171.82 1720.96 L2172.1 1720.96 L2172.1 1720.96 L2171.82 1720.96 L2171.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2171.82,1720.96 2171.82,1720.96 2172.1,1720.96 2171.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2172.1 1720.96 L2172.1 1720.96 L2172.38 1720.96 L2172.38 1720.96 L2172.1 1720.96 L2172.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2172.1,1720.96 2172.1,1720.96 2172.38,1720.96 2172.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2172.38 1720.96 L2172.38 1720.96 L2172.67 1720.96 L2172.67 1720.96 L2172.38 1720.96 L2172.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2172.38,1720.96 2172.38,1720.96 2172.67,1720.96 2172.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2172.67 1720.96 L2172.67 1720.96 L2172.95 1720.96 L2172.95 1720.96 L2172.67 1720.96 L2172.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2172.67,1720.96 2172.67,1720.96 2172.95,1720.96 2172.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2172.95 1720.96 L2172.95 1720.96 L2173.23 1720.96 L2173.23 1720.96 L2172.95 1720.96 L2172.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2172.95,1720.96 2172.95,1720.96 2173.23,1720.96 2172.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2173.23 1720.96 L2173.23 1720.96 L2173.51 1720.96 L2173.51 1720.96 L2173.23 1720.96 L2173.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2173.23,1720.96 2173.23,1720.96 2173.51,1720.96 2173.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2173.51 1720.96 L2173.51 1720.96 L2173.79 1720.96 L2173.79 1720.96 L2173.51 1720.96 L2173.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2173.51,1720.96 2173.51,1720.96 2173.79,1720.96 2173.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2173.79 1720.96 L2173.79 1720.96 L2174.07 1720.96 L2174.07 1720.96 L2173.79 1720.96 L2173.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2173.79,1720.96 2173.79,1720.96 2174.07,1720.96 2173.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2174.07 1720.96 L2174.07 1720.96 L2174.36 1720.96 L2174.36 1720.96 L2174.07 1720.96 L2174.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2174.07,1720.96 2174.07,1720.96 2174.36,1720.96 2174.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2174.36 1720.96 L2174.36 1720.96 L2174.64 1720.96 L2174.64 1720.96 L2174.36 1720.96 L2174.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2174.36,1720.96 2174.36,1720.96 2174.64,1720.96 2174.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2174.64 1720.96 L2174.64 1720.96 L2174.92 1720.96 L2174.92 1720.96 L2174.64 1720.96 L2174.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2174.64,1720.96 2174.64,1720.96 2174.92,1720.96 2174.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2174.92 1720.96 L2174.92 1720.96 L2175.2 1720.96 L2175.2 1720.96 L2174.92 1720.96 L2174.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2174.92,1720.96 2174.92,1720.96 2175.2,1720.96 2174.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2175.2 1720.96 L2175.2 1720.96 L2175.48 1720.96 L2175.48 1720.96 L2175.2 1720.96 L2175.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2175.2,1720.96 2175.2,1720.96 2175.48,1720.96 2175.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2175.48 1720.96 L2175.48 1720.96 L2175.76 1720.96 L2175.76 1720.96 L2175.48 1720.96 L2175.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2175.48,1720.96 2175.48,1720.96 2175.76,1720.96 2175.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2175.76 1720.96 L2175.76 1720.96 L2176.05 1720.96 L2176.05 1720.96 L2175.76 1720.96 L2175.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2175.76,1720.96 2175.76,1720.96 2176.05,1720.96 2175.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2176.05 1720.96 L2176.05 1720.96 L2176.33 1720.96 L2176.33 1720.96 L2176.05 1720.96 L2176.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2176.05,1720.96 2176.05,1720.96 2176.33,1720.96 2176.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2176.33 1720.96 L2176.33 1720.96 L2176.61 1720.96 L2176.61 1720.96 L2176.33 1720.96 L2176.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2176.33,1720.96 2176.33,1720.96 2176.61,1720.96 2176.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2176.61 1720.96 L2176.61 1720.96 L2176.89 1720.96 L2176.89 1720.96 L2176.61 1720.96 L2176.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2176.61,1720.96 2176.61,1720.96 2176.89,1720.96 2176.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2176.89 1720.96 L2176.89 1720.96 L2177.17 1720.96 L2177.17 1720.96 L2176.89 1720.96 L2176.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2176.89,1720.96 2176.89,1720.96 2177.17,1720.96 2176.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2177.17 1720.96 L2177.17 1720.96 L2177.45 1720.96 L2177.45 1720.96 L2177.17 1720.96 L2177.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2177.17,1720.96 2177.17,1720.96 2177.45,1720.96 2177.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2177.45 1720.96 L2177.45 1720.96 L2177.74 1720.96 L2177.74 1720.96 L2177.45 1720.96 L2177.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2177.45,1720.96 2177.45,1720.96 2177.74,1720.96 2177.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2177.74 1720.96 L2177.74 1720.96 L2178.02 1720.96 L2178.02 1720.96 L2177.74 1720.96 L2177.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2177.74,1720.96 2177.74,1720.96 2178.02,1720.96 2177.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2178.02 1720.96 L2178.02 1720.96 L2178.3 1720.96 L2178.3 1720.96 L2178.02 1720.96 L2178.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2178.02,1720.96 2178.02,1720.96 2178.3,1720.96 2178.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2178.3 1720.96 L2178.3 1720.96 L2178.58 1720.96 L2178.58 1720.96 L2178.3 1720.96 L2178.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2178.3,1720.96 2178.3,1720.96 2178.58,1720.96 2178.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2178.58 1720.96 L2178.58 1720.96 L2178.86 1720.96 L2178.86 1720.96 L2178.58 1720.96 L2178.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2178.58,1720.96 2178.58,1720.96 2178.86,1720.96 2178.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2178.86 1720.96 L2178.86 1720.96 L2179.15 1720.96 L2179.15 1720.96 L2178.86 1720.96 L2178.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2178.86,1720.96 2178.86,1720.96 2179.15,1720.96 2178.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2179.15 1720.96 L2179.15 1720.96 L2179.43 1720.96 L2179.43 1720.96 L2179.15 1720.96 L2179.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2179.15,1720.96 2179.15,1720.96 2179.43,1720.96 2179.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2179.43 1720.96 L2179.43 1720.96 L2179.71 1720.96 L2179.71 1720.96 L2179.43 1720.96 L2179.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2179.43,1720.96 2179.43,1720.96 2179.71,1720.96 2179.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2179.71 1720.96 L2179.71 1720.96 L2179.99 1720.96 L2179.99 1720.96 L2179.71 1720.96 L2179.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2179.71,1720.96 2179.71,1720.96 2179.99,1720.96 2179.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2179.99 1720.96 L2179.99 1720.96 L2180.27 1720.96 L2180.27 1720.96 L2179.99 1720.96 L2179.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2179.99,1720.96 2179.99,1720.96 2180.27,1720.96 2179.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2180.27 1720.96 L2180.27 1720.96 L2180.55 1720.96 L2180.55 1720.96 L2180.27 1720.96 L2180.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2180.27,1720.96 2180.27,1720.96 2180.55,1720.96 2180.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2180.55 1720.96 L2180.55 1720.96 L2180.84 1720.96 L2180.84 1720.96 L2180.55 1720.96 L2180.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2180.55,1720.96 2180.55,1720.96 2180.84,1720.96 2180.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2180.84 1720.96 L2180.84 1720.96 L2181.12 1720.96 L2181.12 1720.96 L2180.84 1720.96 L2180.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2180.84,1720.96 2180.84,1720.96 2181.12,1720.96 2180.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2181.12 1720.96 L2181.12 1720.96 L2181.4 1720.96 L2181.4 1720.96 L2181.12 1720.96 L2181.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2181.12,1720.96 2181.12,1720.96 2181.4,1720.96 2181.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2181.4 1720.96 L2181.4 1720.96 L2181.68 1720.96 L2181.68 1720.96 L2181.4 1720.96 L2181.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2181.4,1720.96 2181.4,1720.96 2181.68,1720.96 2181.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2181.68 1720.96 L2181.68 1720.96 L2181.96 1720.96 L2181.96 1720.96 L2181.68 1720.96 L2181.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2181.68,1720.96 2181.68,1720.96 2181.96,1720.96 2181.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2181.96 1720.96 L2181.96 1720.96 L2182.24 1720.96 L2182.24 1720.96 L2181.96 1720.96 L2181.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2181.96,1720.96 2181.96,1720.96 2182.24,1720.96 2181.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2182.24 1720.96 L2182.24 1720.96 L2182.53 1720.96 L2182.53 1720.96 L2182.24 1720.96 L2182.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2182.24,1720.96 2182.24,1720.96 2182.53,1720.96 2182.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2182.53 1720.96 L2182.53 1720.96 L2182.81 1720.96 L2182.81 1720.96 L2182.53 1720.96 L2182.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2182.53,1720.96 2182.53,1720.96 2182.81,1720.96 2182.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2182.81 1720.96 L2182.81 1720.96 L2183.09 1720.96 L2183.09 1720.96 L2182.81 1720.96 L2182.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2182.81,1720.96 2182.81,1720.96 2183.09,1720.96 2182.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2183.09 1720.96 L2183.09 1720.96 L2183.37 1720.96 L2183.37 1720.96 L2183.09 1720.96 L2183.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2183.09,1720.96 2183.09,1720.96 2183.37,1720.96 2183.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2183.37 1720.96 L2183.37 1720.96 L2183.65 1720.96 L2183.65 1720.96 L2183.37 1720.96 L2183.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2183.37,1720.96 2183.37,1720.96 2183.65,1720.96 2183.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2183.65 1720.96 L2183.65 1720.96 L2183.93 1720.96 L2183.93 1720.96 L2183.65 1720.96 L2183.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2183.65,1720.96 2183.65,1720.96 2183.93,1720.96 2183.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2183.93 1720.96 L2183.93 1720.96 L2184.22 1720.96 L2184.22 1720.96 L2183.93 1720.96 L2183.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2183.93,1720.96 2183.93,1720.96 2184.22,1720.96 2183.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2184.22 1720.96 L2184.22 1720.96 L2184.5 1720.96 L2184.5 1720.96 L2184.22 1720.96 L2184.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2184.22,1720.96 2184.22,1720.96 2184.5,1720.96 2184.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2184.5 1720.96 L2184.5 1720.96 L2184.78 1720.96 L2184.78 1720.96 L2184.5 1720.96 L2184.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2184.5,1720.96 2184.5,1720.96 2184.78,1720.96 2184.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2184.78 1720.96 L2184.78 1720.96 L2185.06 1720.96 L2185.06 1720.96 L2184.78 1720.96 L2184.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2184.78,1720.96 2184.78,1720.96 2185.06,1720.96 2184.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2185.06 1720.96 L2185.06 1720.96 L2185.34 1720.96 L2185.34 1720.96 L2185.06 1720.96 L2185.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2185.06,1720.96 2185.06,1720.96 2185.34,1720.96 2185.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2185.34 1720.96 L2185.34 1720.96 L2185.63 1720.96 L2185.63 1720.96 L2185.34 1720.96 L2185.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2185.34,1720.96 2185.34,1720.96 2185.63,1720.96 2185.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2185.63 1720.96 L2185.63 1720.96 L2185.91 1720.96 L2185.91 1720.96 L2185.63 1720.96 L2185.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2185.63,1720.96 2185.63,1720.96 2185.91,1720.96 2185.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2185.91 1720.96 L2185.91 1720.96 L2186.19 1720.96 L2186.19 1720.96 L2185.91 1720.96 L2185.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2185.91,1720.96 2185.91,1720.96 2186.19,1720.96 2185.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2186.19 1720.96 L2186.19 1720.96 L2186.47 1720.96 L2186.47 1720.96 L2186.19 1720.96 L2186.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2186.19,1720.96 2186.19,1720.96 2186.47,1720.96 2186.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2186.47 1720.96 L2186.47 1720.96 L2186.75 1720.96 L2186.75 1720.96 L2186.47 1720.96 L2186.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2186.47,1720.96 2186.47,1720.96 2186.75,1720.96 2186.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2186.75 1720.96 L2186.75 1720.96 L2187.03 1720.96 L2187.03 1720.96 L2186.75 1720.96 L2186.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2186.75,1720.96 2186.75,1720.96 2187.03,1720.96 2186.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2187.03 1720.96 L2187.03 1720.96 L2187.32 1720.96 L2187.32 1720.96 L2187.03 1720.96 L2187.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2187.03,1720.96 2187.03,1720.96 2187.32,1720.96 2187.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2187.32 1720.96 L2187.32 1720.96 L2187.6 1720.96 L2187.6 1720.96 L2187.32 1720.96 L2187.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2187.32,1720.96 2187.32,1720.96 2187.6,1720.96 2187.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2187.6 1720.96 L2187.6 1720.96 L2187.88 1720.96 L2187.88 1720.96 L2187.6 1720.96 L2187.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2187.6,1720.96 2187.6,1720.96 2187.88,1720.96 2187.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2187.88 1720.96 L2187.88 1720.96 L2188.16 1720.96 L2188.16 1720.96 L2187.88 1720.96 L2187.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2187.88,1720.96 2187.88,1720.96 2188.16,1720.96 2187.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2188.16 1720.96 L2188.16 1720.96 L2188.44 1720.96 L2188.44 1720.96 L2188.16 1720.96 L2188.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2188.16,1720.96 2188.16,1720.96 2188.44,1720.96 2188.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2188.44 1720.96 L2188.44 1720.96 L2188.72 1720.96 L2188.72 1720.96 L2188.44 1720.96 L2188.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2188.44,1720.96 2188.44,1720.96 2188.72,1720.96 2188.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2188.72 1720.96 L2188.72 1720.96 L2189.01 1720.96 L2189.01 1720.96 L2188.72 1720.96 L2188.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2188.72,1720.96 2188.72,1720.96 2189.01,1720.96 2188.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2189.01 1720.96 L2189.01 1720.96 L2189.29 1720.96 L2189.29 1720.96 L2189.01 1720.96 L2189.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2189.01,1720.96 2189.01,1720.96 2189.29,1720.96 2189.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2189.29 1720.96 L2189.29 1720.96 L2189.57 1720.96 L2189.57 1720.96 L2189.29 1720.96 L2189.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2189.29,1720.96 2189.29,1720.96 2189.57,1720.96 2189.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2189.57 1720.96 L2189.57 1720.96 L2189.85 1720.96 L2189.85 1720.96 L2189.57 1720.96 L2189.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2189.57,1720.96 2189.57,1720.96 2189.85,1720.96 2189.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2189.85 1720.96 L2189.85 1720.96 L2190.13 1720.96 L2190.13 1720.96 L2189.85 1720.96 L2189.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2189.85,1720.96 2189.85,1720.96 2190.13,1720.96 2189.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2190.13 1720.96 L2190.13 1720.96 L2190.41 1720.96 L2190.41 1720.96 L2190.13 1720.96 L2190.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2190.13,1720.96 2190.13,1720.96 2190.41,1720.96 2190.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2190.41 1720.96 L2190.41 1720.96 L2190.7 1720.96 L2190.7 1720.96 L2190.41 1720.96 L2190.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2190.41,1720.96 2190.41,1720.96 2190.7,1720.96 2190.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2190.7 1720.96 L2190.7 1720.96 L2190.98 1720.96 L2190.98 1720.96 L2190.7 1720.96 L2190.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2190.7,1720.96 2190.7,1720.96 2190.98,1720.96 2190.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2190.98 1720.96 L2190.98 1720.96 L2191.26 1720.96 L2191.26 1720.96 L2190.98 1720.96 L2190.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2190.98,1720.96 2190.98,1720.96 2191.26,1720.96 2190.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2191.26 1720.96 L2191.26 1720.96 L2191.54 1720.96 L2191.54 1720.96 L2191.26 1720.96 L2191.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2191.26,1720.96 2191.26,1720.96 2191.54,1720.96 2191.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2191.54 1720.96 L2191.54 1720.96 L2191.82 1720.96 L2191.82 1720.96 L2191.54 1720.96 L2191.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2191.54,1720.96 2191.54,1720.96 2191.82,1720.96 2191.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2191.82 1720.96 L2191.82 1720.96 L2192.1 1720.96 L2192.1 1720.96 L2191.82 1720.96 L2191.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2191.82,1720.96 2191.82,1720.96 2192.1,1720.96 2191.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2192.1 1720.96 L2192.1 1720.96 L2192.39 1720.96 L2192.39 1720.96 L2192.1 1720.96 L2192.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2192.1,1720.96 2192.1,1720.96 2192.39,1720.96 2192.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2192.39 1720.96 L2192.39 1720.96 L2192.67 1720.96 L2192.67 1720.96 L2192.39 1720.96 L2192.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2192.39,1720.96 2192.39,1720.96 2192.67,1720.96 2192.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2192.67 1720.96 L2192.67 1720.96 L2192.95 1720.96 L2192.95 1720.96 L2192.67 1720.96 L2192.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2192.67,1720.96 2192.67,1720.96 2192.95,1720.96 2192.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2192.95 1720.96 L2192.95 1720.96 L2193.23 1720.96 L2193.23 1720.96 L2192.95 1720.96 L2192.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2192.95,1720.96 2192.95,1720.96 2193.23,1720.96 2192.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2193.23 1720.96 L2193.23 1720.96 L2193.51 1720.96 L2193.51 1720.96 L2193.23 1720.96 L2193.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2193.23,1720.96 2193.23,1720.96 2193.51,1720.96 2193.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2193.51 1720.96 L2193.51 1720.96 L2193.8 1720.96 L2193.8 1720.96 L2193.51 1720.96 L2193.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2193.51,1720.96 2193.51,1720.96 2193.8,1720.96 2193.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2193.8 1720.96 L2193.8 1720.96 L2194.08 1720.96 L2194.08 1720.96 L2193.8 1720.96 L2193.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2193.8,1720.96 2193.8,1720.96 2194.08,1720.96 2193.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2194.08 1720.96 L2194.08 1720.96 L2194.36 1720.96 L2194.36 1720.96 L2194.08 1720.96 L2194.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2194.08,1720.96 2194.08,1720.96 2194.36,1720.96 2194.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2194.36 1720.96 L2194.36 1720.96 L2194.64 1720.96 L2194.64 1720.96 L2194.36 1720.96 L2194.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2194.36,1720.96 2194.36,1720.96 2194.64,1720.96 2194.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2194.64 1720.96 L2194.64 1720.96 L2194.92 1720.96 L2194.92 1720.96 L2194.64 1720.96 L2194.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2194.64,1720.96 2194.64,1720.96 2194.92,1720.96 2194.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2194.92 1720.96 L2194.92 1720.96 L2195.2 1720.96 L2195.2 1720.96 L2194.92 1720.96 L2194.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2194.92,1720.96 2194.92,1720.96 2195.2,1720.96 2194.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2195.2 1720.96 L2195.2 1720.96 L2195.49 1720.96 L2195.49 1720.96 L2195.2 1720.96 L2195.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2195.2,1720.96 2195.2,1720.96 2195.49,1720.96 2195.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2195.49 1720.96 L2195.49 1720.96 L2195.77 1720.96 L2195.77 1720.96 L2195.49 1720.96 L2195.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2195.49,1720.96 2195.49,1720.96 2195.77,1720.96 2195.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2195.77 1720.96 L2195.77 1720.96 L2196.05 1720.96 L2196.05 1720.96 L2195.77 1720.96 L2195.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2195.77,1720.96 2195.77,1720.96 2196.05,1720.96 2195.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2196.05 1720.96 L2196.05 1720.96 L2196.33 1720.96 L2196.33 1720.96 L2196.05 1720.96 L2196.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2196.05,1720.96 2196.05,1720.96 2196.33,1720.96 2196.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2196.33 1720.96 L2196.33 1720.96 L2196.61 1720.96 L2196.61 1720.96 L2196.33 1720.96 L2196.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2196.33,1720.96 2196.33,1720.96 2196.61,1720.96 2196.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2196.61 1720.96 L2196.61 1720.96 L2196.89 1720.96 L2196.89 1720.96 L2196.61 1720.96 L2196.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2196.61,1720.96 2196.61,1720.96 2196.89,1720.96 2196.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2196.89 1720.96 L2196.89 1720.96 L2197.18 1720.96 L2197.18 1720.96 L2196.89 1720.96 L2196.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2196.89,1720.96 2196.89,1720.96 2197.18,1720.96 2196.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2197.18 1720.96 L2197.18 1720.96 L2197.46 1720.96 L2197.46 1720.96 L2197.18 1720.96 L2197.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2197.18,1720.96 2197.18,1720.96 2197.46,1720.96 2197.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2197.46 1720.96 L2197.46 1720.96 L2197.74 1720.96 L2197.74 1720.96 L2197.46 1720.96 L2197.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2197.46,1720.96 2197.46,1720.96 2197.74,1720.96 2197.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2197.74 1720.96 L2197.74 1720.96 L2198.02 1720.96 L2198.02 1720.96 L2197.74 1720.96 L2197.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2197.74,1720.96 2197.74,1720.96 2198.02,1720.96 2197.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2198.02 1720.96 L2198.02 1720.96 L2198.3 1720.96 L2198.3 1720.96 L2198.02 1720.96 L2198.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2198.02,1720.96 2198.02,1720.96 2198.3,1720.96 2198.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2198.3 1720.96 L2198.3 1720.96 L2198.58 1720.96 L2198.58 1720.96 L2198.3 1720.96 L2198.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2198.3,1720.96 2198.3,1720.96 2198.58,1720.96 2198.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2198.58 1720.96 L2198.58 1720.96 L2198.87 1720.96 L2198.87 1720.96 L2198.58 1720.96 L2198.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2198.58,1720.96 2198.58,1720.96 2198.87,1720.96 2198.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2198.87 1720.96 L2198.87 1720.96 L2199.15 1720.96 L2199.15 1720.96 L2198.87 1720.96 L2198.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2198.87,1720.96 2198.87,1720.96 2199.15,1720.96 2198.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2199.15 1720.96 L2199.15 1720.96 L2199.43 1720.96 L2199.43 1720.96 L2199.15 1720.96 L2199.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2199.15,1720.96 2199.15,1720.96 2199.43,1720.96 2199.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2199.43 1720.96 L2199.43 1720.96 L2199.71 1720.96 L2199.71 1720.96 L2199.43 1720.96 L2199.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2199.43,1720.96 2199.43,1720.96 2199.71,1720.96 2199.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2199.71 1720.96 L2199.71 1720.96 L2199.99 1720.96 L2199.99 1720.96 L2199.71 1720.96 L2199.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2199.71,1720.96 2199.71,1720.96 2199.99,1720.96 2199.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2199.99 1720.96 L2199.99 1720.96 L2200.27 1720.96 L2200.27 1720.96 L2199.99 1720.96 L2199.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2199.99,1720.96 2199.99,1720.96 2200.27,1720.96 2199.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2200.27 1720.96 L2200.27 1720.96 L2200.56 1720.96 L2200.56 1720.96 L2200.27 1720.96 L2200.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2200.27,1720.96 2200.27,1720.96 2200.56,1720.96 2200.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2200.56 1720.96 L2200.56 1720.96 L2200.84 1720.96 L2200.84 1720.96 L2200.56 1720.96 L2200.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2200.56,1720.96 2200.56,1720.96 2200.84,1720.96 2200.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2200.84 1720.96 L2200.84 1720.96 L2201.12 1720.96 L2201.12 1720.96 L2200.84 1720.96 L2200.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2200.84,1720.96 2200.84,1720.96 2201.12,1720.96 2200.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2201.12 1720.96 L2201.12 1720.96 L2201.4 1720.96 L2201.4 1720.96 L2201.12 1720.96 L2201.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2201.12,1720.96 2201.12,1720.96 2201.4,1720.96 2201.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2201.4 1720.96 L2201.4 1720.96 L2201.68 1720.96 L2201.68 1720.96 L2201.4 1720.96 L2201.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2201.4,1720.96 2201.4,1720.96 2201.68,1720.96 2201.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2201.68 1720.96 L2201.68 1720.96 L2201.97 1720.96 L2201.97 1720.96 L2201.68 1720.96 L2201.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2201.68,1720.96 2201.68,1720.96 2201.97,1720.96 2201.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2201.97 1720.96 L2201.97 1720.96 L2202.25 1720.96 L2202.25 1720.96 L2201.97 1720.96 L2201.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2201.97,1720.96 2201.97,1720.96 2202.25,1720.96 2201.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2202.25 1720.96 L2202.25 1720.96 L2202.53 1720.96 L2202.53 1720.96 L2202.25 1720.96 L2202.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2202.25,1720.96 2202.25,1720.96 2202.53,1720.96 2202.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2202.53 1720.96 L2202.53 1720.96 L2202.81 1720.96 L2202.81 1720.96 L2202.53 1720.96 L2202.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2202.53,1720.96 2202.53,1720.96 2202.81,1720.96 2202.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2202.81 1720.96 L2202.81 1720.96 L2203.09 1720.96 L2203.09 1720.96 L2202.81 1720.96 L2202.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2202.81,1720.96 2202.81,1720.96 2203.09,1720.96 2202.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2203.09 1720.96 L2203.09 1720.96 L2203.37 1720.96 L2203.37 1720.96 L2203.09 1720.96 L2203.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2203.09,1720.96 2203.09,1720.96 2203.37,1720.96 2203.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2203.37 1720.96 L2203.37 1720.96 L2203.66 1720.96 L2203.66 1720.96 L2203.37 1720.96 L2203.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2203.37,1720.96 2203.37,1720.96 2203.66,1720.96 2203.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2203.66 1720.96 L2203.66 1720.96 L2203.94 1720.96 L2203.94 1720.96 L2203.66 1720.96 L2203.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2203.66,1720.96 2203.66,1720.96 2203.94,1720.96 2203.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2203.94 1720.96 L2203.94 1720.96 L2204.22 1720.96 L2204.22 1720.96 L2203.94 1720.96 L2203.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2203.94,1720.96 2203.94,1720.96 2204.22,1720.96 2203.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2204.22 1720.96 L2204.22 1720.96 L2204.5 1720.96 L2204.5 1720.96 L2204.22 1720.96 L2204.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2204.22,1720.96 2204.22,1720.96 2204.5,1720.96 2204.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2204.5 1720.96 L2204.5 1720.96 L2204.78 1720.96 L2204.78 1720.96 L2204.5 1720.96 L2204.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2204.5,1720.96 2204.5,1720.96 2204.78,1720.96 2204.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2204.78 1720.96 L2204.78 1720.96 L2205.06 1720.96 L2205.06 1720.96 L2204.78 1720.96 L2204.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2204.78,1720.96 2204.78,1720.96 2205.06,1720.96 2204.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2205.06 1720.96 L2205.06 1720.96 L2205.35 1720.96 L2205.35 1720.96 L2205.06 1720.96 L2205.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2205.06,1720.96 2205.06,1720.96 2205.35,1720.96 2205.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2205.35 1720.96 L2205.35 1720.96 L2205.63 1720.96 L2205.63 1720.96 L2205.35 1720.96 L2205.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2205.35,1720.96 2205.35,1720.96 2205.63,1720.96 2205.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2205.63 1720.96 L2205.63 1720.96 L2205.91 1720.96 L2205.91 1720.96 L2205.63 1720.96 L2205.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2205.63,1720.96 2205.63,1720.96 2205.91,1720.96 2205.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2205.91 1720.96 L2205.91 1720.96 L2206.19 1720.96 L2206.19 1720.96 L2205.91 1720.96 L2205.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2205.91,1720.96 2205.91,1720.96 2206.19,1720.96 2205.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2206.19 1720.96 L2206.19 1720.96 L2206.47 1720.96 L2206.47 1720.96 L2206.19 1720.96 L2206.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2206.19,1720.96 2206.19,1720.96 2206.47,1720.96 2206.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2206.47 1720.96 L2206.47 1720.96 L2206.75 1720.96 L2206.75 1720.96 L2206.47 1720.96 L2206.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2206.47,1720.96 2206.47,1720.96 2206.75,1720.96 2206.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2206.75 1720.96 L2206.75 1720.96 L2207.04 1720.96 L2207.04 1720.96 L2206.75 1720.96 L2206.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2206.75,1720.96 2206.75,1720.96 2207.04,1720.96 2206.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2207.04 1720.96 L2207.04 1720.96 L2207.32 1720.96 L2207.32 1720.96 L2207.04 1720.96 L2207.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2207.04,1720.96 2207.04,1720.96 2207.32,1720.96 2207.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2207.32 1720.96 L2207.32 1720.96 L2207.6 1720.96 L2207.6 1720.96 L2207.32 1720.96 L2207.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2207.32,1720.96 2207.32,1720.96 2207.6,1720.96 2207.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2207.6 1720.96 L2207.6 1720.96 L2207.88 1720.96 L2207.88 1720.96 L2207.6 1720.96 L2207.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2207.6,1720.96 2207.6,1720.96 2207.88,1720.96 2207.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2207.88 1720.96 L2207.88 1720.96 L2208.16 1720.96 L2208.16 1720.96 L2207.88 1720.96 L2207.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2207.88,1720.96 2207.88,1720.96 2208.16,1720.96 2207.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2208.16 1720.96 L2208.16 1720.96 L2208.44 1720.96 L2208.44 1720.96 L2208.16 1720.96 L2208.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2208.16,1720.96 2208.16,1720.96 2208.44,1720.96 2208.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2208.44 1720.96 L2208.44 1720.96 L2208.73 1720.96 L2208.73 1720.96 L2208.44 1720.96 L2208.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2208.44,1720.96 2208.44,1720.96 2208.73,1720.96 2208.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2208.73 1720.96 L2208.73 1720.96 L2209.01 1720.96 L2209.01 1720.96 L2208.73 1720.96 L2208.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2208.73,1720.96 2208.73,1720.96 2209.01,1720.96 2208.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2209.01 1720.96 L2209.01 1720.96 L2209.29 1720.96 L2209.29 1720.96 L2209.01 1720.96 L2209.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2209.01,1720.96 2209.01,1720.96 2209.29,1720.96 2209.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2209.29 1720.96 L2209.29 1720.96 L2209.57 1720.96 L2209.57 1720.96 L2209.29 1720.96 L2209.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2209.29,1720.96 2209.29,1720.96 2209.57,1720.96 2209.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2209.57 1720.96 L2209.57 1720.96 L2209.85 1720.96 L2209.85 1720.96 L2209.57 1720.96 L2209.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2209.57,1720.96 2209.57,1720.96 2209.85,1720.96 2209.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2209.85 1720.96 L2209.85 1720.96 L2210.14 1720.96 L2210.14 1720.96 L2209.85 1720.96 L2209.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2209.85,1720.96 2209.85,1720.96 2210.14,1720.96 2209.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2210.14 1720.96 L2210.14 1720.96 L2210.42 1720.96 L2210.42 1720.96 L2210.14 1720.96 L2210.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2210.14,1720.96 2210.14,1720.96 2210.42,1720.96 2210.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2210.42 1720.96 L2210.42 1720.96 L2210.7 1720.96 L2210.7 1720.96 L2210.42 1720.96 L2210.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2210.42,1720.96 2210.42,1720.96 2210.7,1720.96 2210.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2210.7 1720.96 L2210.7 1720.96 L2210.98 1720.96 L2210.98 1720.96 L2210.7 1720.96 L2210.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2210.7,1720.96 2210.7,1720.96 2210.98,1720.96 2210.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2210.98 1720.96 L2210.98 1720.96 L2211.26 1720.96 L2211.26 1720.96 L2210.98 1720.96 L2210.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2210.98,1720.96 2210.98,1720.96 2211.26,1720.96 2210.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2211.26 1720.96 L2211.26 1720.96 L2211.54 1720.96 L2211.54 1720.96 L2211.26 1720.96 L2211.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2211.26,1720.96 2211.26,1720.96 2211.54,1720.96 2211.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2211.54 1720.96 L2211.54 1720.96 L2211.83 1720.96 L2211.83 1720.96 L2211.54 1720.96 L2211.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2211.54,1720.96 2211.54,1720.96 2211.83,1720.96 2211.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2211.83 1720.96 L2211.83 1720.96 L2212.11 1720.96 L2212.11 1720.96 L2211.83 1720.96 L2211.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2211.83,1720.96 2211.83,1720.96 2212.11,1720.96 2211.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2212.11 1720.96 L2212.11 1720.96 L2212.39 1720.96 L2212.39 1720.96 L2212.11 1720.96 L2212.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2212.11,1720.96 2212.11,1720.96 2212.39,1720.96 2212.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2212.39 1720.96 L2212.39 1720.96 L2212.67 1720.96 L2212.67 1720.96 L2212.39 1720.96 L2212.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2212.39,1720.96 2212.39,1720.96 2212.67,1720.96 2212.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2212.67 1720.96 L2212.67 1720.96 L2212.95 1720.96 L2212.95 1720.96 L2212.67 1720.96 L2212.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2212.67,1720.96 2212.67,1720.96 2212.95,1720.96 2212.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2212.95 1720.96 L2212.95 1720.96 L2213.23 1720.96 L2213.23 1720.96 L2212.95 1720.96 L2212.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2212.95,1720.96 2212.95,1720.96 2213.23,1720.96 2212.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2213.23 1720.96 L2213.23 1720.96 L2213.52 1720.96 L2213.52 1720.96 L2213.23 1720.96 L2213.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2213.23,1720.96 2213.23,1720.96 2213.52,1720.96 2213.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2213.52 1720.96 L2213.52 1720.96 L2213.8 1720.96 L2213.8 1720.96 L2213.52 1720.96 L2213.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2213.52,1720.96 2213.52,1720.96 2213.8,1720.96 2213.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2213.8 1720.96 L2213.8 1720.96 L2214.08 1720.96 L2214.08 1720.96 L2213.8 1720.96 L2213.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2213.8,1720.96 2213.8,1720.96 2214.08,1720.96 2213.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2214.08 1720.96 L2214.08 1720.96 L2214.36 1720.96 L2214.36 1720.96 L2214.08 1720.96 L2214.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2214.08,1720.96 2214.08,1720.96 2214.36,1720.96 2214.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2214.36 1720.96 L2214.36 1720.96 L2214.64 1720.96 L2214.64 1720.96 L2214.36 1720.96 L2214.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2214.36,1720.96 2214.36,1720.96 2214.64,1720.96 2214.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2214.64 1720.96 L2214.64 1720.96 L2214.92 1720.96 L2214.92 1720.96 L2214.64 1720.96 L2214.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2214.64,1720.96 2214.64,1720.96 2214.92,1720.96 2214.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2214.92 1720.96 L2214.92 1720.96 L2215.21 1720.96 L2215.21 1720.96 L2214.92 1720.96 L2214.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2214.92,1720.96 2214.92,1720.96 2215.21,1720.96 2214.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2215.21 1720.96 L2215.21 1720.96 L2215.49 1720.96 L2215.49 1720.96 L2215.21 1720.96 L2215.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2215.21,1720.96 2215.21,1720.96 2215.49,1720.96 2215.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2215.49 1720.96 L2215.49 1720.96 L2215.77 1720.96 L2215.77 1720.96 L2215.49 1720.96 L2215.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2215.49,1720.96 2215.49,1720.96 2215.77,1720.96 2215.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2215.77 1720.96 L2215.77 1720.96 L2216.05 1720.96 L2216.05 1720.96 L2215.77 1720.96 L2215.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2215.77,1720.96 2215.77,1720.96 2216.05,1720.96 2215.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2216.05 1720.96 L2216.05 1720.96 L2216.33 1720.96 L2216.33 1720.96 L2216.05 1720.96 L2216.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2216.05,1720.96 2216.05,1720.96 2216.33,1720.96 2216.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2216.33 1720.96 L2216.33 1720.96 L2216.61 1720.96 L2216.61 1720.96 L2216.33 1720.96 L2216.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2216.33,1720.96 2216.33,1720.96 2216.61,1720.96 2216.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2216.61 1720.96 L2216.61 1720.96 L2216.9 1720.96 L2216.9 1720.96 L2216.61 1720.96 L2216.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2216.61,1720.96 2216.61,1720.96 2216.9,1720.96 2216.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2216.9 1720.96 L2216.9 1720.96 L2217.18 1720.96 L2217.18 1720.96 L2216.9 1720.96 L2216.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2216.9,1720.96 2216.9,1720.96 2217.18,1720.96 2216.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2217.18 1720.96 L2217.18 1720.96 L2217.46 1720.96 L2217.46 1720.96 L2217.18 1720.96 L2217.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2217.18,1720.96 2217.18,1720.96 2217.46,1720.96 2217.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2217.46 1720.96 L2217.46 1720.96 L2217.74 1720.96 L2217.74 1720.96 L2217.46 1720.96 L2217.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2217.46,1720.96 2217.46,1720.96 2217.74,1720.96 2217.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2217.74 1720.96 L2217.74 1720.96 L2218.02 1720.96 L2218.02 1720.96 L2217.74 1720.96 L2217.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2217.74,1720.96 2217.74,1720.96 2218.02,1720.96 2217.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2218.02 1720.96 L2218.02 1720.96 L2218.31 1720.96 L2218.31 1720.96 L2218.02 1720.96 L2218.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2218.02,1720.96 2218.02,1720.96 2218.31,1720.96 2218.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2218.31 1720.96 L2218.31 1720.96 L2218.59 1720.96 L2218.59 1720.96 L2218.31 1720.96 L2218.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2218.31,1720.96 2218.31,1720.96 2218.59,1720.96 2218.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2218.59 1720.96 L2218.59 1720.96 L2218.87 1720.96 L2218.87 1720.96 L2218.59 1720.96 L2218.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2218.59,1720.96 2218.59,1720.96 2218.87,1720.96 2218.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2218.87 1720.96 L2218.87 1720.96 L2219.15 1720.96 L2219.15 1720.96 L2218.87 1720.96 L2218.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2218.87,1720.96 2218.87,1720.96 2219.15,1720.96 2218.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2219.15 1720.96 L2219.15 1720.96 L2219.43 1720.96 L2219.43 1720.96 L2219.15 1720.96 L2219.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2219.15,1720.96 2219.15,1720.96 2219.43,1720.96 2219.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2219.43 1720.96 L2219.43 1720.96 L2219.71 1720.96 L2219.71 1720.96 L2219.43 1720.96 L2219.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2219.43,1720.96 2219.43,1720.96 2219.71,1720.96 2219.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2219.71 1720.96 L2219.71 1720.96 L2220 1720.96 L2220 1720.96 L2219.71 1720.96 L2219.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2219.71,1720.96 2219.71,1720.96 2220,1720.96 2219.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2220 1720.96 L2220 1720.96 L2220.28 1720.96 L2220.28 1720.96 L2220 1720.96 L2220 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2220,1720.96 2220,1720.96 2220.28,1720.96 2220,1720.96 "/>
<path clip-path="url(#clip322)" d="M2220.28 1720.96 L2220.28 1720.96 L2220.56 1720.96 L2220.56 1720.96 L2220.28 1720.96 L2220.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2220.28,1720.96 2220.28,1720.96 2220.56,1720.96 2220.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2220.56 1720.96 L2220.56 1720.96 L2220.84 1720.96 L2220.84 1720.96 L2220.56 1720.96 L2220.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2220.56,1720.96 2220.56,1720.96 2220.84,1720.96 2220.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2220.84 1720.96 L2220.84 1720.96 L2221.12 1720.96 L2221.12 1720.96 L2220.84 1720.96 L2220.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2220.84,1720.96 2220.84,1720.96 2221.12,1720.96 2220.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2221.12 1720.96 L2221.12 1720.96 L2221.4 1720.96 L2221.4 1720.96 L2221.12 1720.96 L2221.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2221.12,1720.96 2221.12,1720.96 2221.4,1720.96 2221.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2221.4 1720.96 L2221.4 1720.96 L2221.69 1720.96 L2221.69 1720.96 L2221.4 1720.96 L2221.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2221.4,1720.96 2221.4,1720.96 2221.69,1720.96 2221.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2221.69 1720.96 L2221.69 1720.96 L2221.97 1720.96 L2221.97 1720.96 L2221.69 1720.96 L2221.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2221.69,1720.96 2221.69,1720.96 2221.97,1720.96 2221.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2221.97 1720.96 L2221.97 1720.96 L2222.25 1720.96 L2222.25 1720.96 L2221.97 1720.96 L2221.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2221.97,1720.96 2221.97,1720.96 2222.25,1720.96 2221.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2222.25 1720.96 L2222.25 1720.96 L2222.53 1720.96 L2222.53 1720.96 L2222.25 1720.96 L2222.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2222.25,1720.96 2222.25,1720.96 2222.53,1720.96 2222.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2222.53 1720.96 L2222.53 1720.96 L2222.81 1720.96 L2222.81 1720.96 L2222.53 1720.96 L2222.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2222.53,1720.96 2222.53,1720.96 2222.81,1720.96 2222.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2222.81 1720.96 L2222.81 1720.96 L2223.09 1720.96 L2223.09 1720.96 L2222.81 1720.96 L2222.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2222.81,1720.96 2222.81,1720.96 2223.09,1720.96 2222.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2223.09 1720.96 L2223.09 1720.96 L2223.38 1720.96 L2223.38 1720.96 L2223.09 1720.96 L2223.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2223.09,1720.96 2223.09,1720.96 2223.38,1720.96 2223.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2223.38 1720.96 L2223.38 1720.96 L2223.66 1720.96 L2223.66 1720.96 L2223.38 1720.96 L2223.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2223.38,1720.96 2223.38,1720.96 2223.66,1720.96 2223.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2223.66 1720.96 L2223.66 1720.96 L2223.94 1720.96 L2223.94 1720.96 L2223.66 1720.96 L2223.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2223.66,1720.96 2223.66,1720.96 2223.94,1720.96 2223.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2223.94 1720.96 L2223.94 1720.96 L2224.22 1720.96 L2224.22 1720.96 L2223.94 1720.96 L2223.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2223.94,1720.96 2223.94,1720.96 2224.22,1720.96 2223.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2224.22 1720.96 L2224.22 1720.96 L2224.5 1720.96 L2224.5 1720.96 L2224.22 1720.96 L2224.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2224.22,1720.96 2224.22,1720.96 2224.5,1720.96 2224.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2224.5 1720.96 L2224.5 1720.96 L2224.78 1720.96 L2224.78 1720.96 L2224.5 1720.96 L2224.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2224.5,1720.96 2224.5,1720.96 2224.78,1720.96 2224.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2224.78 1720.96 L2224.78 1720.96 L2225.07 1720.96 L2225.07 1720.96 L2224.78 1720.96 L2224.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2224.78,1720.96 2224.78,1720.96 2225.07,1720.96 2224.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2225.07 1720.96 L2225.07 1720.96 L2225.35 1720.96 L2225.35 1720.96 L2225.07 1720.96 L2225.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2225.07,1720.96 2225.07,1720.96 2225.35,1720.96 2225.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2225.35 1720.96 L2225.35 1720.96 L2225.63 1720.96 L2225.63 1720.96 L2225.35 1720.96 L2225.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2225.35,1720.96 2225.35,1720.96 2225.63,1720.96 2225.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2225.63 1720.96 L2225.63 1720.96 L2225.91 1720.96 L2225.91 1720.96 L2225.63 1720.96 L2225.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2225.63,1720.96 2225.63,1720.96 2225.91,1720.96 2225.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2225.91 1720.96 L2225.91 1720.96 L2226.19 1720.96 L2226.19 1720.96 L2225.91 1720.96 L2225.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2225.91,1720.96 2225.91,1720.96 2226.19,1720.96 2225.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2226.19 1720.96 L2226.19 1720.96 L2226.48 1720.96 L2226.48 1720.96 L2226.19 1720.96 L2226.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2226.19,1720.96 2226.19,1720.96 2226.48,1720.96 2226.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2226.48 1720.96 L2226.48 1720.96 L2226.76 1720.96 L2226.76 1720.96 L2226.48 1720.96 L2226.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2226.48,1720.96 2226.48,1720.96 2226.76,1720.96 2226.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2226.76 1720.96 L2226.76 1720.96 L2227.04 1720.96 L2227.04 1720.96 L2226.76 1720.96 L2226.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2226.76,1720.96 2226.76,1720.96 2227.04,1720.96 2226.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2227.04 1720.96 L2227.04 1720.96 L2227.32 1720.96 L2227.32 1720.96 L2227.04 1720.96 L2227.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2227.04,1720.96 2227.04,1720.96 2227.32,1720.96 2227.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2227.32 1720.96 L2227.32 1720.96 L2227.6 1720.96 L2227.6 1720.96 L2227.32 1720.96 L2227.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2227.32,1720.96 2227.32,1720.96 2227.6,1720.96 2227.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2227.6 1720.96 L2227.6 1720.96 L2227.88 1720.96 L2227.88 1720.96 L2227.6 1720.96 L2227.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2227.6,1720.96 2227.6,1720.96 2227.88,1720.96 2227.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2227.88 1720.96 L2227.88 1720.96 L2228.17 1720.96 L2228.17 1720.96 L2227.88 1720.96 L2227.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2227.88,1720.96 2227.88,1720.96 2228.17,1720.96 2227.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2228.17 1720.96 L2228.17 1720.96 L2228.45 1720.96 L2228.45 1720.96 L2228.17 1720.96 L2228.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2228.17,1720.96 2228.17,1720.96 2228.45,1720.96 2228.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2228.45 1720.96 L2228.45 1720.96 L2228.73 1720.96 L2228.73 1720.96 L2228.45 1720.96 L2228.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2228.45,1720.96 2228.45,1720.96 2228.73,1720.96 2228.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2228.73 1720.96 L2228.73 1720.96 L2229.01 1720.96 L2229.01 1720.96 L2228.73 1720.96 L2228.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2228.73,1720.96 2228.73,1720.96 2229.01,1720.96 2228.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2229.01 1720.96 L2229.01 1720.96 L2229.29 1720.96 L2229.29 1720.96 L2229.01 1720.96 L2229.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2229.01,1720.96 2229.01,1720.96 2229.29,1720.96 2229.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2229.29 1720.96 L2229.29 1720.96 L2229.57 1720.96 L2229.57 1720.96 L2229.29 1720.96 L2229.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2229.29,1720.96 2229.29,1720.96 2229.57,1720.96 2229.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2229.57 1720.96 L2229.57 1720.96 L2229.86 1720.96 L2229.86 1720.96 L2229.57 1720.96 L2229.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2229.57,1720.96 2229.57,1720.96 2229.86,1720.96 2229.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2229.86 1720.96 L2229.86 1720.96 L2230.14 1720.96 L2230.14 1720.96 L2229.86 1720.96 L2229.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2229.86,1720.96 2229.86,1720.96 2230.14,1720.96 2229.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2230.14 1720.96 L2230.14 1720.96 L2230.42 1720.96 L2230.42 1720.96 L2230.14 1720.96 L2230.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2230.14,1720.96 2230.14,1720.96 2230.42,1720.96 2230.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2230.42 1720.96 L2230.42 1720.96 L2230.7 1720.96 L2230.7 1720.96 L2230.42 1720.96 L2230.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2230.42,1720.96 2230.42,1720.96 2230.7,1720.96 2230.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2230.7 1720.96 L2230.7 1720.96 L2230.98 1720.96 L2230.98 1720.96 L2230.7 1720.96 L2230.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2230.7,1720.96 2230.7,1720.96 2230.98,1720.96 2230.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2230.98 1720.96 L2230.98 1720.96 L2231.26 1720.96 L2231.26 1720.96 L2230.98 1720.96 L2230.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2230.98,1720.96 2230.98,1720.96 2231.26,1720.96 2230.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2231.26 1720.96 L2231.26 1720.96 L2231.55 1720.96 L2231.55 1720.96 L2231.26 1720.96 L2231.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2231.26,1720.96 2231.26,1720.96 2231.55,1720.96 2231.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2231.55 1720.96 L2231.55 1720.96 L2231.83 1720.96 L2231.83 1720.96 L2231.55 1720.96 L2231.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2231.55,1720.96 2231.55,1720.96 2231.83,1720.96 2231.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2231.83 1720.96 L2231.83 1720.96 L2232.11 1720.96 L2232.11 1720.96 L2231.83 1720.96 L2231.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2231.83,1720.96 2231.83,1720.96 2232.11,1720.96 2231.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2232.11 1720.96 L2232.11 1720.96 L2232.39 1720.96 L2232.39 1720.96 L2232.11 1720.96 L2232.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2232.11,1720.96 2232.11,1720.96 2232.39,1720.96 2232.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2232.39 1720.96 L2232.39 1720.96 L2232.67 1720.96 L2232.67 1720.96 L2232.39 1720.96 L2232.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2232.39,1720.96 2232.39,1720.96 2232.67,1720.96 2232.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2232.67 1720.96 L2232.67 1720.96 L2232.95 1720.96 L2232.95 1720.96 L2232.67 1720.96 L2232.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2232.67,1720.96 2232.67,1720.96 2232.95,1720.96 2232.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2232.95 1720.96 L2232.95 1720.96 L2233.24 1720.96 L2233.24 1720.96 L2232.95 1720.96 L2232.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2232.95,1720.96 2232.95,1720.96 2233.24,1720.96 2232.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2233.24 1720.96 L2233.24 1720.96 L2233.52 1720.96 L2233.52 1720.96 L2233.24 1720.96 L2233.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2233.24,1720.96 2233.24,1720.96 2233.52,1720.96 2233.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2233.52 1720.96 L2233.52 1720.96 L2233.8 1720.96 L2233.8 1720.96 L2233.52 1720.96 L2233.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2233.52,1720.96 2233.52,1720.96 2233.8,1720.96 2233.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2233.8 1720.96 L2233.8 1720.96 L2234.08 1720.96 L2234.08 1720.96 L2233.8 1720.96 L2233.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2233.8,1720.96 2233.8,1720.96 2234.08,1720.96 2233.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2234.08 1720.96 L2234.08 1720.96 L2234.36 1720.96 L2234.36 1720.96 L2234.08 1720.96 L2234.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2234.08,1720.96 2234.08,1720.96 2234.36,1720.96 2234.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2234.36 1720.96 L2234.36 1720.96 L2234.65 1720.96 L2234.65 1720.96 L2234.36 1720.96 L2234.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2234.36,1720.96 2234.36,1720.96 2234.65,1720.96 2234.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2234.65 1720.96 L2234.65 1720.96 L2234.93 1720.96 L2234.93 1720.96 L2234.65 1720.96 L2234.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2234.65,1720.96 2234.65,1720.96 2234.93,1720.96 2234.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2234.93 1720.96 L2234.93 1720.96 L2235.21 1720.96 L2235.21 1720.96 L2234.93 1720.96 L2234.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2234.93,1720.96 2234.93,1720.96 2235.21,1720.96 2234.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2235.21 1720.96 L2235.21 1720.96 L2235.49 1720.96 L2235.49 1720.96 L2235.21 1720.96 L2235.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2235.21,1720.96 2235.21,1720.96 2235.49,1720.96 2235.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2235.49 1720.96 L2235.49 1720.96 L2235.77 1720.96 L2235.77 1720.96 L2235.49 1720.96 L2235.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2235.49,1720.96 2235.49,1720.96 2235.77,1720.96 2235.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2235.77 1720.96 L2235.77 1720.96 L2236.05 1720.96 L2236.05 1720.96 L2235.77 1720.96 L2235.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2235.77,1720.96 2235.77,1720.96 2236.05,1720.96 2235.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2236.05 1720.96 L2236.05 1720.96 L2236.34 1720.96 L2236.34 1720.96 L2236.05 1720.96 L2236.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2236.05,1720.96 2236.05,1720.96 2236.34,1720.96 2236.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2236.34 1720.96 L2236.34 1720.96 L2236.62 1720.96 L2236.62 1720.96 L2236.34 1720.96 L2236.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2236.34,1720.96 2236.34,1720.96 2236.62,1720.96 2236.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2236.62 1720.96 L2236.62 1720.96 L2236.9 1720.96 L2236.9 1720.96 L2236.62 1720.96 L2236.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2236.62,1720.96 2236.62,1720.96 2236.9,1720.96 2236.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2236.9 1720.96 L2236.9 1720.96 L2237.18 1720.96 L2237.18 1720.96 L2236.9 1720.96 L2236.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2236.9,1720.96 2236.9,1720.96 2237.18,1720.96 2236.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2237.18 1720.96 L2237.18 1720.96 L2237.46 1720.96 L2237.46 1720.96 L2237.18 1720.96 L2237.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2237.18,1720.96 2237.18,1720.96 2237.46,1720.96 2237.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2237.46 1720.96 L2237.46 1720.96 L2237.74 1720.96 L2237.74 1720.96 L2237.46 1720.96 L2237.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2237.46,1720.96 2237.46,1720.96 2237.74,1720.96 2237.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2237.74 1720.96 L2237.74 1720.96 L2238.03 1720.96 L2238.03 1720.96 L2237.74 1720.96 L2237.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2237.74,1720.96 2237.74,1720.96 2238.03,1720.96 2237.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2238.03 1720.96 L2238.03 1720.96 L2238.31 1720.96 L2238.31 1720.96 L2238.03 1720.96 L2238.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2238.03,1720.96 2238.03,1720.96 2238.31,1720.96 2238.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2238.31 1720.96 L2238.31 1720.96 L2238.59 1720.96 L2238.59 1720.96 L2238.31 1720.96 L2238.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2238.31,1720.96 2238.31,1720.96 2238.59,1720.96 2238.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2238.59 1720.96 L2238.59 1720.96 L2238.87 1720.96 L2238.87 1720.96 L2238.59 1720.96 L2238.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2238.59,1720.96 2238.59,1720.96 2238.87,1720.96 2238.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2238.87 1720.96 L2238.87 1720.96 L2239.15 1720.96 L2239.15 1720.96 L2238.87 1720.96 L2238.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2238.87,1720.96 2238.87,1720.96 2239.15,1720.96 2238.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2239.15 1720.96 L2239.15 1720.96 L2239.43 1720.96 L2239.43 1720.96 L2239.15 1720.96 L2239.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2239.15,1720.96 2239.15,1720.96 2239.43,1720.96 2239.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2239.43 1720.96 L2239.43 1720.96 L2239.72 1720.96 L2239.72 1720.96 L2239.43 1720.96 L2239.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2239.43,1720.96 2239.43,1720.96 2239.72,1720.96 2239.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2239.72 1720.96 L2239.72 1720.96 L2240 1720.96 L2240 1720.96 L2239.72 1720.96 L2239.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2239.72,1720.96 2239.72,1720.96 2240,1720.96 2239.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2240 1720.96 L2240 1720.96 L2240.28 1720.96 L2240.28 1720.96 L2240 1720.96 L2240 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2240,1720.96 2240,1720.96 2240.28,1720.96 2240,1720.96 "/>
<path clip-path="url(#clip322)" d="M2240.28 1720.96 L2240.28 1720.96 L2240.56 1720.96 L2240.56 1720.96 L2240.28 1720.96 L2240.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2240.28,1720.96 2240.28,1720.96 2240.56,1720.96 2240.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2240.56 1720.96 L2240.56 1720.96 L2240.84 1720.96 L2240.84 1720.96 L2240.56 1720.96 L2240.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2240.56,1720.96 2240.56,1720.96 2240.84,1720.96 2240.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2240.84 1720.96 L2240.84 1720.96 L2241.12 1720.96 L2241.12 1720.96 L2240.84 1720.96 L2240.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2240.84,1720.96 2240.84,1720.96 2241.12,1720.96 2240.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2241.12 1720.96 L2241.12 1720.96 L2241.41 1720.96 L2241.41 1720.96 L2241.12 1720.96 L2241.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2241.12,1720.96 2241.12,1720.96 2241.41,1720.96 2241.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2241.41 1720.96 L2241.41 1720.96 L2241.69 1720.96 L2241.69 1720.96 L2241.41 1720.96 L2241.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2241.41,1720.96 2241.41,1720.96 2241.69,1720.96 2241.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2241.69 1720.96 L2241.69 1720.96 L2241.97 1720.96 L2241.97 1720.96 L2241.69 1720.96 L2241.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2241.69,1720.96 2241.69,1720.96 2241.97,1720.96 2241.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2241.97 1720.96 L2241.97 1720.96 L2242.25 1720.96 L2242.25 1720.96 L2241.97 1720.96 L2241.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2241.97,1720.96 2241.97,1720.96 2242.25,1720.96 2241.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2242.25 1720.96 L2242.25 1720.96 L2242.53 1720.96 L2242.53 1720.96 L2242.25 1720.96 L2242.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2242.25,1720.96 2242.25,1720.96 2242.53,1720.96 2242.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2242.53 1720.96 L2242.53 1720.96 L2242.82 1720.96 L2242.82 1720.96 L2242.53 1720.96 L2242.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2242.53,1720.96 2242.53,1720.96 2242.82,1720.96 2242.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2242.82 1720.96 L2242.82 1720.96 L2243.1 1720.96 L2243.1 1720.96 L2242.82 1720.96 L2242.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2242.82,1720.96 2242.82,1720.96 2243.1,1720.96 2242.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2243.1 1720.96 L2243.1 1720.96 L2243.38 1720.96 L2243.38 1720.96 L2243.1 1720.96 L2243.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2243.1,1720.96 2243.1,1720.96 2243.38,1720.96 2243.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2243.38 1720.96 L2243.38 1720.96 L2243.66 1720.96 L2243.66 1720.96 L2243.38 1720.96 L2243.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2243.38,1720.96 2243.38,1720.96 2243.66,1720.96 2243.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2243.66 1720.96 L2243.66 1720.96 L2243.94 1720.96 L2243.94 1720.96 L2243.66 1720.96 L2243.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2243.66,1720.96 2243.66,1720.96 2243.94,1720.96 2243.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2243.94 1720.96 L2243.94 1720.96 L2244.22 1720.96 L2244.22 1720.96 L2243.94 1720.96 L2243.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2243.94,1720.96 2243.94,1720.96 2244.22,1720.96 2243.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2244.22 1720.96 L2244.22 1720.96 L2244.51 1720.96 L2244.51 1720.96 L2244.22 1720.96 L2244.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2244.22,1720.96 2244.22,1720.96 2244.51,1720.96 2244.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2244.51 1720.96 L2244.51 1720.96 L2244.79 1720.96 L2244.79 1720.96 L2244.51 1720.96 L2244.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2244.51,1720.96 2244.51,1720.96 2244.79,1720.96 2244.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2244.79 1720.96 L2244.79 1720.96 L2245.07 1720.96 L2245.07 1720.96 L2244.79 1720.96 L2244.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2244.79,1720.96 2244.79,1720.96 2245.07,1720.96 2244.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2245.07 1720.96 L2245.07 1720.96 L2245.35 1720.96 L2245.35 1720.96 L2245.07 1720.96 L2245.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2245.07,1720.96 2245.07,1720.96 2245.35,1720.96 2245.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2245.35 1720.96 L2245.35 1720.96 L2245.63 1720.96 L2245.63 1720.96 L2245.35 1720.96 L2245.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2245.35,1720.96 2245.35,1720.96 2245.63,1720.96 2245.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2245.63 1720.96 L2245.63 1720.96 L2245.91 1720.96 L2245.91 1720.96 L2245.63 1720.96 L2245.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2245.63,1720.96 2245.63,1720.96 2245.91,1720.96 2245.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2245.91 1720.96 L2245.91 1720.96 L2246.2 1720.96 L2246.2 1720.96 L2245.91 1720.96 L2245.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2245.91,1720.96 2245.91,1720.96 2246.2,1720.96 2245.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2246.2 1720.96 L2246.2 1720.96 L2246.48 1720.96 L2246.48 1720.96 L2246.2 1720.96 L2246.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2246.2,1720.96 2246.2,1720.96 2246.48,1720.96 2246.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2246.48 1720.96 L2246.48 1720.96 L2246.76 1720.96 L2246.76 1720.96 L2246.48 1720.96 L2246.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2246.48,1720.96 2246.48,1720.96 2246.76,1720.96 2246.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2246.76 1720.96 L2246.76 1720.96 L2247.04 1720.96 L2247.04 1720.96 L2246.76 1720.96 L2246.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2246.76,1720.96 2246.76,1720.96 2247.04,1720.96 2246.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2247.04 1720.96 L2247.04 1720.96 L2247.32 1720.96 L2247.32 1720.96 L2247.04 1720.96 L2247.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2247.04,1720.96 2247.04,1720.96 2247.32,1720.96 2247.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2247.32 1720.96 L2247.32 1720.96 L2247.6 1720.96 L2247.6 1720.96 L2247.32 1720.96 L2247.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2247.32,1720.96 2247.32,1720.96 2247.6,1720.96 2247.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2247.6 1720.96 L2247.6 1720.96 L2247.89 1720.96 L2247.89 1720.96 L2247.6 1720.96 L2247.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2247.6,1720.96 2247.6,1720.96 2247.89,1720.96 2247.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2247.89 1720.96 L2247.89 1720.96 L2248.17 1720.96 L2248.17 1720.96 L2247.89 1720.96 L2247.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2247.89,1720.96 2247.89,1720.96 2248.17,1720.96 2247.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2248.17 1720.96 L2248.17 1720.96 L2248.45 1720.96 L2248.45 1720.96 L2248.17 1720.96 L2248.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2248.17,1720.96 2248.17,1720.96 2248.45,1720.96 2248.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2248.45 1720.96 L2248.45 1720.96 L2248.73 1720.96 L2248.73 1720.96 L2248.45 1720.96 L2248.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2248.45,1720.96 2248.45,1720.96 2248.73,1720.96 2248.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2248.73 1720.96 L2248.73 1720.96 L2249.01 1720.96 L2249.01 1720.96 L2248.73 1720.96 L2248.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2248.73,1720.96 2248.73,1720.96 2249.01,1720.96 2248.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2249.01 1720.96 L2249.01 1720.96 L2249.3 1720.96 L2249.3 1720.96 L2249.01 1720.96 L2249.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2249.01,1720.96 2249.01,1720.96 2249.3,1720.96 2249.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2249.3 1720.96 L2249.3 1720.96 L2249.58 1720.96 L2249.58 1720.96 L2249.3 1720.96 L2249.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2249.3,1720.96 2249.3,1720.96 2249.58,1720.96 2249.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2249.58 1720.96 L2249.58 1720.96 L2249.86 1720.96 L2249.86 1720.96 L2249.58 1720.96 L2249.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2249.58,1720.96 2249.58,1720.96 2249.86,1720.96 2249.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2249.86 1720.96 L2249.86 1720.96 L2250.14 1720.96 L2250.14 1720.96 L2249.86 1720.96 L2249.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2249.86,1720.96 2249.86,1720.96 2250.14,1720.96 2249.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2250.14 1720.96 L2250.14 1720.96 L2250.42 1720.96 L2250.42 1720.96 L2250.14 1720.96 L2250.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2250.14,1720.96 2250.14,1720.96 2250.42,1720.96 2250.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2250.42 1720.96 L2250.42 1720.96 L2250.7 1720.96 L2250.7 1720.96 L2250.42 1720.96 L2250.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2250.42,1720.96 2250.42,1720.96 2250.7,1720.96 2250.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2250.7 1720.96 L2250.7 1720.96 L2250.99 1720.96 L2250.99 1720.96 L2250.7 1720.96 L2250.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2250.7,1720.96 2250.7,1720.96 2250.99,1720.96 2250.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2250.99 1720.96 L2250.99 1720.96 L2251.27 1720.96 L2251.27 1720.96 L2250.99 1720.96 L2250.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2250.99,1720.96 2250.99,1720.96 2251.27,1720.96 2250.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2251.27 1720.96 L2251.27 1720.96 L2251.55 1720.96 L2251.55 1720.96 L2251.27 1720.96 L2251.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2251.27,1720.96 2251.27,1720.96 2251.55,1720.96 2251.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2251.55 1720.96 L2251.55 1720.96 L2251.83 1720.96 L2251.83 1720.96 L2251.55 1720.96 L2251.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2251.55,1720.96 2251.55,1720.96 2251.83,1720.96 2251.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2251.83 1720.96 L2251.83 1720.96 L2252.11 1720.96 L2252.11 1720.96 L2251.83 1720.96 L2251.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2251.83,1720.96 2251.83,1720.96 2252.11,1720.96 2251.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2252.11 1720.96 L2252.11 1720.96 L2252.39 1720.96 L2252.39 1720.96 L2252.11 1720.96 L2252.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2252.11,1720.96 2252.11,1720.96 2252.39,1720.96 2252.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2252.39 1720.96 L2252.39 1720.96 L2252.68 1720.96 L2252.68 1720.96 L2252.39 1720.96 L2252.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2252.39,1720.96 2252.39,1720.96 2252.68,1720.96 2252.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2252.68 1720.96 L2252.68 1720.96 L2252.96 1720.96 L2252.96 1720.96 L2252.68 1720.96 L2252.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2252.68,1720.96 2252.68,1720.96 2252.96,1720.96 2252.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2252.96 1720.96 L2252.96 1720.96 L2253.24 1720.96 L2253.24 1720.96 L2252.96 1720.96 L2252.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2252.96,1720.96 2252.96,1720.96 2253.24,1720.96 2252.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2253.24 1720.96 L2253.24 1720.96 L2253.52 1720.96 L2253.52 1720.96 L2253.24 1720.96 L2253.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2253.24,1720.96 2253.24,1720.96 2253.52,1720.96 2253.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2253.52 1720.96 L2253.52 1720.96 L2253.8 1720.96 L2253.8 1720.96 L2253.52 1720.96 L2253.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2253.52,1720.96 2253.52,1720.96 2253.8,1720.96 2253.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2253.8 1720.96 L2253.8 1720.96 L2254.08 1720.96 L2254.08 1720.96 L2253.8 1720.96 L2253.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2253.8,1720.96 2253.8,1720.96 2254.08,1720.96 2253.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2254.08 1720.96 L2254.08 1720.96 L2254.37 1720.96 L2254.37 1720.96 L2254.08 1720.96 L2254.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2254.08,1720.96 2254.08,1720.96 2254.37,1720.96 2254.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2254.37 1720.96 L2254.37 1720.96 L2254.65 1720.96 L2254.65 1720.96 L2254.37 1720.96 L2254.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2254.37,1720.96 2254.37,1720.96 2254.65,1720.96 2254.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2254.65 1720.96 L2254.65 1720.96 L2254.93 1720.96 L2254.93 1720.96 L2254.65 1720.96 L2254.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2254.65,1720.96 2254.65,1720.96 2254.93,1720.96 2254.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2254.93 1720.96 L2254.93 1720.96 L2255.21 1720.96 L2255.21 1720.96 L2254.93 1720.96 L2254.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2254.93,1720.96 2254.93,1720.96 2255.21,1720.96 2254.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2255.21 1720.96 L2255.21 1720.96 L2255.49 1720.96 L2255.49 1720.96 L2255.21 1720.96 L2255.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2255.21,1720.96 2255.21,1720.96 2255.49,1720.96 2255.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2255.49 1720.96 L2255.49 1720.96 L2255.77 1720.96 L2255.77 1720.96 L2255.49 1720.96 L2255.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2255.49,1720.96 2255.49,1720.96 2255.77,1720.96 2255.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2255.77 1720.96 L2255.77 1720.96 L2256.06 1720.96 L2256.06 1720.96 L2255.77 1720.96 L2255.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2255.77,1720.96 2255.77,1720.96 2256.06,1720.96 2255.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2256.06 1720.96 L2256.06 1720.96 L2256.34 1720.96 L2256.34 1720.96 L2256.06 1720.96 L2256.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2256.06,1720.96 2256.06,1720.96 2256.34,1720.96 2256.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2256.34 1720.96 L2256.34 1720.96 L2256.62 1720.96 L2256.62 1720.96 L2256.34 1720.96 L2256.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2256.34,1720.96 2256.34,1720.96 2256.62,1720.96 2256.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2256.62 1720.96 L2256.62 1720.96 L2256.9 1720.96 L2256.9 1720.96 L2256.62 1720.96 L2256.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2256.62,1720.96 2256.62,1720.96 2256.9,1720.96 2256.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2256.9 1720.96 L2256.9 1720.96 L2257.18 1720.96 L2257.18 1720.96 L2256.9 1720.96 L2256.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2256.9,1720.96 2256.9,1720.96 2257.18,1720.96 2256.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2257.18 1720.96 L2257.18 1720.96 L2257.47 1720.96 L2257.47 1720.96 L2257.18 1720.96 L2257.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2257.18,1720.96 2257.18,1720.96 2257.47,1720.96 2257.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2257.47 1720.96 L2257.47 1720.96 L2257.75 1720.96 L2257.75 1720.96 L2257.47 1720.96 L2257.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2257.47,1720.96 2257.47,1720.96 2257.75,1720.96 2257.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2257.75 1720.96 L2257.75 1720.96 L2258.03 1720.96 L2258.03 1720.96 L2257.75 1720.96 L2257.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2257.75,1720.96 2257.75,1720.96 2258.03,1720.96 2257.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2258.03 1720.96 L2258.03 1720.96 L2258.31 1720.96 L2258.31 1720.96 L2258.03 1720.96 L2258.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2258.03,1720.96 2258.03,1720.96 2258.31,1720.96 2258.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2258.31 1720.96 L2258.31 1720.96 L2258.59 1720.96 L2258.59 1720.96 L2258.31 1720.96 L2258.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2258.31,1720.96 2258.31,1720.96 2258.59,1720.96 2258.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2258.59 1720.96 L2258.59 1720.96 L2258.87 1720.96 L2258.87 1720.96 L2258.59 1720.96 L2258.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2258.59,1720.96 2258.59,1720.96 2258.87,1720.96 2258.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2258.87 1720.96 L2258.87 1720.96 L2259.16 1720.96 L2259.16 1720.96 L2258.87 1720.96 L2258.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2258.87,1720.96 2258.87,1720.96 2259.16,1720.96 2258.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2259.16 1720.96 L2259.16 1720.96 L2259.44 1720.96 L2259.44 1720.96 L2259.16 1720.96 L2259.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2259.16,1720.96 2259.16,1720.96 2259.44,1720.96 2259.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2259.44 1720.96 L2259.44 1720.96 L2259.72 1720.96 L2259.72 1720.96 L2259.44 1720.96 L2259.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2259.44,1720.96 2259.44,1720.96 2259.72,1720.96 2259.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2259.72 1720.96 L2259.72 1720.96 L2260 1720.96 L2260 1720.96 L2259.72 1720.96 L2259.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2259.72,1720.96 2259.72,1720.96 2260,1720.96 2259.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2260 1720.96 L2260 1720.96 L2260.28 1720.96 L2260.28 1720.96 L2260 1720.96 L2260 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2260,1720.96 2260,1720.96 2260.28,1720.96 2260,1720.96 "/>
<path clip-path="url(#clip322)" d="M2260.28 1720.96 L2260.28 1720.96 L2260.56 1720.96 L2260.56 1720.96 L2260.28 1720.96 L2260.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2260.28,1720.96 2260.28,1720.96 2260.56,1720.96 2260.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2260.56 1720.96 L2260.56 1720.96 L2260.85 1720.96 L2260.85 1720.96 L2260.56 1720.96 L2260.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2260.56,1720.96 2260.56,1720.96 2260.85,1720.96 2260.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2260.85 1720.96 L2260.85 1720.96 L2261.13 1720.96 L2261.13 1720.96 L2260.85 1720.96 L2260.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2260.85,1720.96 2260.85,1720.96 2261.13,1720.96 2260.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2261.13 1720.96 L2261.13 1720.96 L2261.41 1720.96 L2261.41 1720.96 L2261.13 1720.96 L2261.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2261.13,1720.96 2261.13,1720.96 2261.41,1720.96 2261.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2261.41 1720.96 L2261.41 1720.96 L2261.69 1720.96 L2261.69 1720.96 L2261.41 1720.96 L2261.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2261.41,1720.96 2261.41,1720.96 2261.69,1720.96 2261.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2261.69 1720.96 L2261.69 1720.96 L2261.97 1720.96 L2261.97 1720.96 L2261.69 1720.96 L2261.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2261.69,1720.96 2261.69,1720.96 2261.97,1720.96 2261.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2261.97 1720.96 L2261.97 1720.96 L2262.25 1720.96 L2262.25 1720.96 L2261.97 1720.96 L2261.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2261.97,1720.96 2261.97,1720.96 2262.25,1720.96 2261.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2262.25 1720.96 L2262.25 1720.96 L2262.54 1720.96 L2262.54 1720.96 L2262.25 1720.96 L2262.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2262.25,1720.96 2262.25,1720.96 2262.54,1720.96 2262.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2262.54 1720.96 L2262.54 1720.96 L2262.82 1720.96 L2262.82 1720.96 L2262.54 1720.96 L2262.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2262.54,1720.96 2262.54,1720.96 2262.82,1720.96 2262.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2262.82 1720.96 L2262.82 1720.96 L2263.1 1720.96 L2263.1 1720.96 L2262.82 1720.96 L2262.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2262.82,1720.96 2262.82,1720.96 2263.1,1720.96 2262.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2263.1 1720.96 L2263.1 1720.96 L2263.38 1720.96 L2263.38 1720.96 L2263.1 1720.96 L2263.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2263.1,1720.96 2263.1,1720.96 2263.38,1720.96 2263.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2263.38 1720.96 L2263.38 1720.96 L2263.66 1720.96 L2263.66 1720.96 L2263.38 1720.96 L2263.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2263.38,1720.96 2263.38,1720.96 2263.66,1720.96 2263.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2263.66 1720.96 L2263.66 1720.96 L2263.94 1720.96 L2263.94 1720.96 L2263.66 1720.96 L2263.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2263.66,1720.96 2263.66,1720.96 2263.94,1720.96 2263.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2263.94 1720.96 L2263.94 1720.96 L2264.23 1720.96 L2264.23 1720.96 L2263.94 1720.96 L2263.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2263.94,1720.96 2263.94,1720.96 2264.23,1720.96 2263.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2264.23 1720.96 L2264.23 1720.96 L2264.51 1720.96 L2264.51 1720.96 L2264.23 1720.96 L2264.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2264.23,1720.96 2264.23,1720.96 2264.51,1720.96 2264.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2264.51 1720.96 L2264.51 1720.96 L2264.79 1720.96 L2264.79 1720.96 L2264.51 1720.96 L2264.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2264.51,1720.96 2264.51,1720.96 2264.79,1720.96 2264.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2264.79 1720.96 L2264.79 1720.96 L2265.07 1720.96 L2265.07 1720.96 L2264.79 1720.96 L2264.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2264.79,1720.96 2264.79,1720.96 2265.07,1720.96 2264.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2265.07 1720.96 L2265.07 1720.96 L2265.35 1720.96 L2265.35 1720.96 L2265.07 1720.96 L2265.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2265.07,1720.96 2265.07,1720.96 2265.35,1720.96 2265.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2265.35 1720.96 L2265.35 1720.96 L2265.64 1720.96 L2265.64 1720.96 L2265.35 1720.96 L2265.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2265.35,1720.96 2265.35,1720.96 2265.64,1720.96 2265.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2265.64 1720.96 L2265.64 1720.96 L2265.92 1720.96 L2265.92 1720.96 L2265.64 1720.96 L2265.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2265.64,1720.96 2265.64,1720.96 2265.92,1720.96 2265.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2265.92 1720.96 L2265.92 1720.96 L2266.2 1720.96 L2266.2 1720.96 L2265.92 1720.96 L2265.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2265.92,1720.96 2265.92,1720.96 2266.2,1720.96 2265.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2266.2 1720.96 L2266.2 1720.96 L2266.48 1720.96 L2266.48 1720.96 L2266.2 1720.96 L2266.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2266.2,1720.96 2266.2,1720.96 2266.48,1720.96 2266.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2266.48 1720.96 L2266.48 1720.96 L2266.76 1720.96 L2266.76 1720.96 L2266.48 1720.96 L2266.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2266.48,1720.96 2266.48,1720.96 2266.76,1720.96 2266.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2266.76 1720.96 L2266.76 1720.96 L2267.04 1720.96 L2267.04 1720.96 L2266.76 1720.96 L2266.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2266.76,1720.96 2266.76,1720.96 2267.04,1720.96 2266.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2267.04 1720.96 L2267.04 1720.96 L2267.33 1720.96 L2267.33 1720.96 L2267.04 1720.96 L2267.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2267.04,1720.96 2267.04,1720.96 2267.33,1720.96 2267.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2267.33 1720.96 L2267.33 1720.96 L2267.61 1720.96 L2267.61 1720.96 L2267.33 1720.96 L2267.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2267.33,1720.96 2267.33,1720.96 2267.61,1720.96 2267.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2267.61 1720.96 L2267.61 1720.96 L2267.89 1720.96 L2267.89 1720.96 L2267.61 1720.96 L2267.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2267.61,1720.96 2267.61,1720.96 2267.89,1720.96 2267.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2267.89 1720.96 L2267.89 1720.96 L2268.17 1720.96 L2268.17 1720.96 L2267.89 1720.96 L2267.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2267.89,1720.96 2267.89,1720.96 2268.17,1720.96 2267.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2268.17 1720.96 L2268.17 1720.96 L2268.45 1720.96 L2268.45 1720.96 L2268.17 1720.96 L2268.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2268.17,1720.96 2268.17,1720.96 2268.45,1720.96 2268.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2268.45 1720.96 L2268.45 1720.96 L2268.73 1720.96 L2268.73 1720.96 L2268.45 1720.96 L2268.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2268.45,1720.96 2268.45,1720.96 2268.73,1720.96 2268.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2268.73 1720.96 L2268.73 1720.96 L2269.02 1720.96 L2269.02 1720.96 L2268.73 1720.96 L2268.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2268.73,1720.96 2268.73,1720.96 2269.02,1720.96 2268.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2269.02 1720.96 L2269.02 1720.96 L2269.3 1720.96 L2269.3 1720.96 L2269.02 1720.96 L2269.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2269.02,1720.96 2269.02,1720.96 2269.3,1720.96 2269.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2269.3 1720.96 L2269.3 1720.96 L2269.58 1720.96 L2269.58 1720.96 L2269.3 1720.96 L2269.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2269.3,1720.96 2269.3,1720.96 2269.58,1720.96 2269.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2269.58 1720.96 L2269.58 1720.96 L2269.86 1720.96 L2269.86 1720.96 L2269.58 1720.96 L2269.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2269.58,1720.96 2269.58,1720.96 2269.86,1720.96 2269.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2269.86 1720.96 L2269.86 1720.96 L2270.14 1720.96 L2270.14 1720.96 L2269.86 1720.96 L2269.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2269.86,1720.96 2269.86,1720.96 2270.14,1720.96 2269.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2270.14 1720.96 L2270.14 1720.96 L2270.42 1720.96 L2270.42 1720.96 L2270.14 1720.96 L2270.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2270.14,1720.96 2270.14,1720.96 2270.42,1720.96 2270.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2270.42 1720.96 L2270.42 1720.96 L2270.71 1720.96 L2270.71 1720.96 L2270.42 1720.96 L2270.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2270.42,1720.96 2270.42,1720.96 2270.71,1720.96 2270.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2270.71 1720.96 L2270.71 1720.96 L2270.99 1720.96 L2270.99 1720.96 L2270.71 1720.96 L2270.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2270.71,1720.96 2270.71,1720.96 2270.99,1720.96 2270.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2270.99 1720.96 L2270.99 1720.96 L2271.27 1720.96 L2271.27 1720.96 L2270.99 1720.96 L2270.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2270.99,1720.96 2270.99,1720.96 2271.27,1720.96 2270.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2271.27 1720.96 L2271.27 1720.96 L2271.55 1720.96 L2271.55 1720.96 L2271.27 1720.96 L2271.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2271.27,1720.96 2271.27,1720.96 2271.55,1720.96 2271.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2271.55 1720.96 L2271.55 1720.96 L2271.83 1720.96 L2271.83 1720.96 L2271.55 1720.96 L2271.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2271.55,1720.96 2271.55,1720.96 2271.83,1720.96 2271.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2271.83 1720.96 L2271.83 1720.96 L2272.11 1720.96 L2272.11 1720.96 L2271.83 1720.96 L2271.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2271.83,1720.96 2271.83,1720.96 2272.11,1720.96 2271.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2272.11 1720.96 L2272.11 1720.96 L2272.4 1720.96 L2272.4 1720.96 L2272.11 1720.96 L2272.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2272.11,1720.96 2272.11,1720.96 2272.4,1720.96 2272.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2272.4 1720.96 L2272.4 1720.96 L2272.68 1720.96 L2272.68 1720.96 L2272.4 1720.96 L2272.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2272.4,1720.96 2272.4,1720.96 2272.68,1720.96 2272.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2272.68 1720.96 L2272.68 1720.96 L2272.96 1720.96 L2272.96 1720.96 L2272.68 1720.96 L2272.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2272.68,1720.96 2272.68,1720.96 2272.96,1720.96 2272.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2272.96 1720.96 L2272.96 1720.96 L2273.24 1720.96 L2273.24 1720.96 L2272.96 1720.96 L2272.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2272.96,1720.96 2272.96,1720.96 2273.24,1720.96 2272.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2273.24 1720.96 L2273.24 1720.96 L2273.52 1720.96 L2273.52 1720.96 L2273.24 1720.96 L2273.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2273.24,1720.96 2273.24,1720.96 2273.52,1720.96 2273.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2273.52 1720.96 L2273.52 1720.96 L2273.81 1720.96 L2273.81 1720.96 L2273.52 1720.96 L2273.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2273.52,1720.96 2273.52,1720.96 2273.81,1720.96 2273.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2273.81 1720.96 L2273.81 1720.96 L2274.09 1720.96 L2274.09 1720.96 L2273.81 1720.96 L2273.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2273.81,1720.96 2273.81,1720.96 2274.09,1720.96 2273.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2274.09 1720.96 L2274.09 1720.96 L2274.37 1720.96 L2274.37 1720.96 L2274.09 1720.96 L2274.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2274.09,1720.96 2274.09,1720.96 2274.37,1720.96 2274.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2274.37 1720.96 L2274.37 1720.96 L2274.65 1720.96 L2274.65 1720.96 L2274.37 1720.96 L2274.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2274.37,1720.96 2274.37,1720.96 2274.65,1720.96 2274.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2274.65 1720.96 L2274.65 1720.96 L2274.93 1720.96 L2274.93 1720.96 L2274.65 1720.96 L2274.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2274.65,1720.96 2274.65,1720.96 2274.93,1720.96 2274.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2274.93 1720.96 L2274.93 1720.96 L2275.21 1720.96 L2275.21 1720.96 L2274.93 1720.96 L2274.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2274.93,1720.96 2274.93,1720.96 2275.21,1720.96 2274.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2275.21 1720.96 L2275.21 1720.96 L2275.5 1720.96 L2275.5 1720.96 L2275.21 1720.96 L2275.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2275.21,1720.96 2275.21,1720.96 2275.5,1720.96 2275.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2275.5 1720.96 L2275.5 1720.96 L2275.78 1720.96 L2275.78 1720.96 L2275.5 1720.96 L2275.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2275.5,1720.96 2275.5,1720.96 2275.78,1720.96 2275.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2275.78 1720.96 L2275.78 1720.96 L2276.06 1720.96 L2276.06 1720.96 L2275.78 1720.96 L2275.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2275.78,1720.96 2275.78,1720.96 2276.06,1720.96 2275.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2276.06 1720.96 L2276.06 1720.96 L2276.34 1720.96 L2276.34 1720.96 L2276.06 1720.96 L2276.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2276.06,1720.96 2276.06,1720.96 2276.34,1720.96 2276.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2276.34 1720.96 L2276.34 1720.96 L2276.62 1720.96 L2276.62 1720.96 L2276.34 1720.96 L2276.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2276.34,1720.96 2276.34,1720.96 2276.62,1720.96 2276.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2276.62 1720.96 L2276.62 1720.96 L2276.9 1720.96 L2276.9 1720.96 L2276.62 1720.96 L2276.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2276.62,1720.96 2276.62,1720.96 2276.9,1720.96 2276.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2276.9 1720.96 L2276.9 1720.96 L2277.19 1720.96 L2277.19 1720.96 L2276.9 1720.96 L2276.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2276.9,1720.96 2276.9,1720.96 2277.19,1720.96 2276.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2277.19 1720.96 L2277.19 1720.96 L2277.47 1720.96 L2277.47 1720.96 L2277.19 1720.96 L2277.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2277.19,1720.96 2277.19,1720.96 2277.47,1720.96 2277.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2277.47 1720.96 L2277.47 1720.96 L2277.75 1720.96 L2277.75 1720.96 L2277.47 1720.96 L2277.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2277.47,1720.96 2277.47,1720.96 2277.75,1720.96 2277.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2277.75 1720.96 L2277.75 1720.96 L2278.03 1720.96 L2278.03 1720.96 L2277.75 1720.96 L2277.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2277.75,1720.96 2277.75,1720.96 2278.03,1720.96 2277.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2278.03 1720.96 L2278.03 1720.96 L2278.31 1720.96 L2278.31 1720.96 L2278.03 1720.96 L2278.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2278.03,1720.96 2278.03,1720.96 2278.31,1720.96 2278.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2278.31 1720.96 L2278.31 1720.96 L2278.59 1720.96 L2278.59 1720.96 L2278.31 1720.96 L2278.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2278.31,1720.96 2278.31,1720.96 2278.59,1720.96 2278.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2278.59 1720.96 L2278.59 1720.96 L2278.88 1720.96 L2278.88 1720.96 L2278.59 1720.96 L2278.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2278.59,1720.96 2278.59,1720.96 2278.88,1720.96 2278.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2278.88 1720.96 L2278.88 1720.96 L2279.16 1720.96 L2279.16 1720.96 L2278.88 1720.96 L2278.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2278.88,1720.96 2278.88,1720.96 2279.16,1720.96 2278.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2279.16 1720.96 L2279.16 1720.96 L2279.44 1720.96 L2279.44 1720.96 L2279.16 1720.96 L2279.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2279.16,1720.96 2279.16,1720.96 2279.44,1720.96 2279.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2279.44 1720.96 L2279.44 1720.96 L2279.72 1720.96 L2279.72 1720.96 L2279.44 1720.96 L2279.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2279.44,1720.96 2279.44,1720.96 2279.72,1720.96 2279.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2279.72 1720.96 L2279.72 1720.96 L2280 1720.96 L2280 1720.96 L2279.72 1720.96 L2279.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2279.72,1720.96 2279.72,1720.96 2280,1720.96 2279.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2280 1720.96 L2280 1720.96 L2280.28 1720.96 L2280.28 1720.96 L2280 1720.96 L2280 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2280,1720.96 2280,1720.96 2280.28,1720.96 2280,1720.96 "/>
<path clip-path="url(#clip322)" d="M2280.28 1720.96 L2280.28 1720.96 L2280.57 1720.96 L2280.57 1720.96 L2280.28 1720.96 L2280.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2280.28,1720.96 2280.28,1720.96 2280.57,1720.96 2280.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2280.57 1720.96 L2280.57 1720.96 L2280.85 1720.96 L2280.85 1720.96 L2280.57 1720.96 L2280.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2280.57,1720.96 2280.57,1720.96 2280.85,1720.96 2280.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2280.85 1720.96 L2280.85 1720.96 L2281.13 1720.96 L2281.13 1720.96 L2280.85 1720.96 L2280.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2280.85,1720.96 2280.85,1720.96 2281.13,1720.96 2280.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2281.13 1720.96 L2281.13 1720.96 L2281.41 1720.96 L2281.41 1720.96 L2281.13 1720.96 L2281.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2281.13,1720.96 2281.13,1720.96 2281.41,1720.96 2281.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2281.41 1720.96 L2281.41 1720.96 L2281.69 1720.96 L2281.69 1720.96 L2281.41 1720.96 L2281.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2281.41,1720.96 2281.41,1720.96 2281.69,1720.96 2281.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2281.69 1720.96 L2281.69 1720.96 L2281.98 1720.96 L2281.98 1720.96 L2281.69 1720.96 L2281.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2281.69,1720.96 2281.69,1720.96 2281.98,1720.96 2281.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2281.98 1720.96 L2281.98 1720.96 L2282.26 1720.96 L2282.26 1720.96 L2281.98 1720.96 L2281.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2281.98,1720.96 2281.98,1720.96 2282.26,1720.96 2281.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2282.26 1720.96 L2282.26 1720.96 L2282.54 1720.96 L2282.54 1720.96 L2282.26 1720.96 L2282.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2282.26,1720.96 2282.26,1720.96 2282.54,1720.96 2282.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2282.54 1720.96 L2282.54 1720.96 L2282.82 1720.96 L2282.82 1720.96 L2282.54 1720.96 L2282.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2282.54,1720.96 2282.54,1720.96 2282.82,1720.96 2282.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2282.82 1720.96 L2282.82 1720.96 L2283.1 1720.96 L2283.1 1720.96 L2282.82 1720.96 L2282.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2282.82,1720.96 2282.82,1720.96 2283.1,1720.96 2282.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2283.1 1720.96 L2283.1 1720.96 L2283.38 1720.96 L2283.38 1720.96 L2283.1 1720.96 L2283.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2283.1,1720.96 2283.1,1720.96 2283.38,1720.96 2283.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2283.38 1720.96 L2283.38 1720.96 L2283.67 1720.96 L2283.67 1720.96 L2283.38 1720.96 L2283.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2283.38,1720.96 2283.38,1720.96 2283.67,1720.96 2283.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2283.67 1720.96 L2283.67 1720.96 L2283.95 1720.96 L2283.95 1720.96 L2283.67 1720.96 L2283.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2283.67,1720.96 2283.67,1720.96 2283.95,1720.96 2283.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2283.95 1720.96 L2283.95 1720.96 L2284.23 1720.96 L2284.23 1720.96 L2283.95 1720.96 L2283.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2283.95,1720.96 2283.95,1720.96 2284.23,1720.96 2283.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2284.23 1720.96 L2284.23 1720.96 L2284.51 1720.96 L2284.51 1720.96 L2284.23 1720.96 L2284.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2284.23,1720.96 2284.23,1720.96 2284.51,1720.96 2284.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2284.51 1720.96 L2284.51 1720.96 L2284.79 1720.96 L2284.79 1720.96 L2284.51 1720.96 L2284.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2284.51,1720.96 2284.51,1720.96 2284.79,1720.96 2284.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2284.79 1720.96 L2284.79 1720.96 L2285.07 1720.96 L2285.07 1720.96 L2284.79 1720.96 L2284.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2284.79,1720.96 2284.79,1720.96 2285.07,1720.96 2284.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2285.07 1720.96 L2285.07 1720.96 L2285.36 1720.96 L2285.36 1720.96 L2285.07 1720.96 L2285.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2285.07,1720.96 2285.07,1720.96 2285.36,1720.96 2285.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2285.36 1720.96 L2285.36 1720.96 L2285.64 1720.96 L2285.64 1720.96 L2285.36 1720.96 L2285.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2285.36,1720.96 2285.36,1720.96 2285.64,1720.96 2285.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2285.64 1720.96 L2285.64 1720.96 L2285.92 1720.96 L2285.92 1720.96 L2285.64 1720.96 L2285.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2285.64,1720.96 2285.64,1720.96 2285.92,1720.96 2285.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2285.92 1720.96 L2285.92 1720.96 L2286.2 1720.96 L2286.2 1720.96 L2285.92 1720.96 L2285.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2285.92,1720.96 2285.92,1720.96 2286.2,1720.96 2285.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2286.2 1720.96 L2286.2 1720.96 L2286.48 1720.96 L2286.48 1720.96 L2286.2 1720.96 L2286.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2286.2,1720.96 2286.2,1720.96 2286.48,1720.96 2286.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2286.48 1720.96 L2286.48 1720.96 L2286.76 1720.96 L2286.76 1720.96 L2286.48 1720.96 L2286.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2286.48,1720.96 2286.48,1720.96 2286.76,1720.96 2286.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2286.76 1720.96 L2286.76 1720.96 L2287.05 1720.96 L2287.05 1720.96 L2286.76 1720.96 L2286.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2286.76,1720.96 2286.76,1720.96 2287.05,1720.96 2286.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2287.05 1720.96 L2287.05 1720.96 L2287.33 1720.96 L2287.33 1720.96 L2287.05 1720.96 L2287.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2287.05,1720.96 2287.05,1720.96 2287.33,1720.96 2287.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2287.33 1720.96 L2287.33 1720.96 L2287.61 1720.96 L2287.61 1720.96 L2287.33 1720.96 L2287.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2287.33,1720.96 2287.33,1720.96 2287.61,1720.96 2287.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2287.61 1720.96 L2287.61 1720.96 L2287.89 1720.96 L2287.89 1720.96 L2287.61 1720.96 L2287.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2287.61,1720.96 2287.61,1720.96 2287.89,1720.96 2287.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2287.89 1720.96 L2287.89 1720.96 L2288.17 1720.96 L2288.17 1720.96 L2287.89 1720.96 L2287.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2287.89,1720.96 2287.89,1720.96 2288.17,1720.96 2287.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2288.17 1720.96 L2288.17 1720.96 L2288.45 1720.96 L2288.45 1720.96 L2288.17 1720.96 L2288.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2288.17,1720.96 2288.17,1720.96 2288.45,1720.96 2288.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2288.45 1720.96 L2288.45 1720.96 L2288.74 1720.96 L2288.74 1720.96 L2288.45 1720.96 L2288.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2288.45,1720.96 2288.45,1720.96 2288.74,1720.96 2288.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2288.74 1720.96 L2288.74 1720.96 L2289.02 1720.96 L2289.02 1720.96 L2288.74 1720.96 L2288.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2288.74,1720.96 2288.74,1720.96 2289.02,1720.96 2288.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2289.02 1720.96 L2289.02 1720.96 L2289.3 1720.96 L2289.3 1720.96 L2289.02 1720.96 L2289.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2289.02,1720.96 2289.02,1720.96 2289.3,1720.96 2289.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2289.3 1720.96 L2289.3 1720.96 L2289.58 1720.96 L2289.58 1720.96 L2289.3 1720.96 L2289.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2289.3,1720.96 2289.3,1720.96 2289.58,1720.96 2289.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2289.58 1720.96 L2289.58 1720.96 L2289.86 1720.96 L2289.86 1720.96 L2289.58 1720.96 L2289.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2289.58,1720.96 2289.58,1720.96 2289.86,1720.96 2289.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2289.86 1720.96 L2289.86 1720.96 L2290.15 1720.96 L2290.15 1720.96 L2289.86 1720.96 L2289.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2289.86,1720.96 2289.86,1720.96 2290.15,1720.96 2289.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2290.15 1720.96 L2290.15 1720.96 L2290.43 1720.96 L2290.43 1720.96 L2290.15 1720.96 L2290.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2290.15,1720.96 2290.15,1720.96 2290.43,1720.96 2290.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2290.43 1720.96 L2290.43 1720.96 L2290.71 1720.96 L2290.71 1720.96 L2290.43 1720.96 L2290.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2290.43,1720.96 2290.43,1720.96 2290.71,1720.96 2290.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2290.71 1720.96 L2290.71 1720.96 L2290.99 1720.96 L2290.99 1720.96 L2290.71 1720.96 L2290.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2290.71,1720.96 2290.71,1720.96 2290.99,1720.96 2290.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2290.99 1720.96 L2290.99 1720.96 L2291.27 1720.96 L2291.27 1720.96 L2290.99 1720.96 L2290.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2290.99,1720.96 2290.99,1720.96 2291.27,1720.96 2290.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2291.27 1720.96 L2291.27 1720.96 L2291.55 1720.96 L2291.55 1720.96 L2291.27 1720.96 L2291.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2291.27,1720.96 2291.27,1720.96 2291.55,1720.96 2291.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2291.55 1720.96 L2291.55 1720.96 L2291.84 1720.96 L2291.84 1720.96 L2291.55 1720.96 L2291.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2291.55,1720.96 2291.55,1720.96 2291.84,1720.96 2291.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2291.84 1720.96 L2291.84 1720.96 L2292.12 1720.96 L2292.12 1720.96 L2291.84 1720.96 L2291.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2291.84,1720.96 2291.84,1720.96 2292.12,1720.96 2291.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2292.12 1720.96 L2292.12 1720.96 L2292.4 1720.96 L2292.4 1720.96 L2292.12 1720.96 L2292.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2292.12,1720.96 2292.12,1720.96 2292.4,1720.96 2292.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2292.4 1720.96 L2292.4 1720.96 L2292.68 1720.96 L2292.68 1720.96 L2292.4 1720.96 L2292.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2292.4,1720.96 2292.4,1720.96 2292.68,1720.96 2292.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2292.68 1720.96 L2292.68 1720.96 L2292.96 1720.96 L2292.96 1720.96 L2292.68 1720.96 L2292.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2292.68,1720.96 2292.68,1720.96 2292.96,1720.96 2292.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2292.96 1720.96 L2292.96 1720.96 L2293.24 1720.96 L2293.24 1720.96 L2292.96 1720.96 L2292.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2292.96,1720.96 2292.96,1720.96 2293.24,1720.96 2292.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2293.24 1720.96 L2293.24 1720.96 L2293.53 1720.96 L2293.53 1720.96 L2293.24 1720.96 L2293.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2293.24,1720.96 2293.24,1720.96 2293.53,1720.96 2293.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2293.53 1720.96 L2293.53 1720.96 L2293.81 1720.96 L2293.81 1720.96 L2293.53 1720.96 L2293.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2293.53,1720.96 2293.53,1720.96 2293.81,1720.96 2293.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2293.81 1720.96 L2293.81 1720.96 L2294.09 1720.96 L2294.09 1720.96 L2293.81 1720.96 L2293.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2293.81,1720.96 2293.81,1720.96 2294.09,1720.96 2293.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2294.09 1720.96 L2294.09 1720.96 L2294.37 1720.96 L2294.37 1720.96 L2294.09 1720.96 L2294.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2294.09,1720.96 2294.09,1720.96 2294.37,1720.96 2294.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2294.37 1720.96 L2294.37 1720.96 L2294.65 1720.96 L2294.65 1720.96 L2294.37 1720.96 L2294.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2294.37,1720.96 2294.37,1720.96 2294.65,1720.96 2294.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2294.65 1720.96 L2294.65 1720.96 L2294.93 1720.96 L2294.93 1720.96 L2294.65 1720.96 L2294.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2294.65,1720.96 2294.65,1720.96 2294.93,1720.96 2294.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2294.93 1720.96 L2294.93 1720.96 L2295.22 1720.96 L2295.22 1720.96 L2294.93 1720.96 L2294.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2294.93,1720.96 2294.93,1720.96 2295.22,1720.96 2294.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2295.22 1720.96 L2295.22 1720.96 L2295.5 1720.96 L2295.5 1720.96 L2295.22 1720.96 L2295.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2295.22,1720.96 2295.22,1720.96 2295.5,1720.96 2295.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2295.5 1720.96 L2295.5 1720.96 L2295.78 1720.96 L2295.78 1720.96 L2295.5 1720.96 L2295.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2295.5,1720.96 2295.5,1720.96 2295.78,1720.96 2295.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2295.78 1720.96 L2295.78 1720.96 L2296.06 1720.96 L2296.06 1720.96 L2295.78 1720.96 L2295.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2295.78,1720.96 2295.78,1720.96 2296.06,1720.96 2295.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2296.06 1720.96 L2296.06 1720.96 L2296.34 1720.96 L2296.34 1720.96 L2296.06 1720.96 L2296.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2296.06,1720.96 2296.06,1720.96 2296.34,1720.96 2296.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2296.34 1720.96 L2296.34 1720.96 L2296.62 1720.96 L2296.62 1720.96 L2296.34 1720.96 L2296.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2296.34,1720.96 2296.34,1720.96 2296.62,1720.96 2296.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2296.62 1720.96 L2296.62 1720.96 L2296.91 1720.96 L2296.91 1720.96 L2296.62 1720.96 L2296.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2296.62,1720.96 2296.62,1720.96 2296.91,1720.96 2296.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2296.91 1720.96 L2296.91 1720.96 L2297.19 1720.96 L2297.19 1720.96 L2296.91 1720.96 L2296.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2296.91,1720.96 2296.91,1720.96 2297.19,1720.96 2296.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2297.19 1720.96 L2297.19 1720.96 L2297.47 1720.96 L2297.47 1720.96 L2297.19 1720.96 L2297.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2297.19,1720.96 2297.19,1720.96 2297.47,1720.96 2297.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2297.47 1720.96 L2297.47 1720.96 L2297.75 1720.96 L2297.75 1720.96 L2297.47 1720.96 L2297.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2297.47,1720.96 2297.47,1720.96 2297.75,1720.96 2297.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2297.75 1720.96 L2297.75 1720.96 L2298.03 1720.96 L2298.03 1720.96 L2297.75 1720.96 L2297.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2297.75,1720.96 2297.75,1720.96 2298.03,1720.96 2297.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2298.03 1720.96 L2298.03 1720.96 L2298.32 1720.96 L2298.32 1720.96 L2298.03 1720.96 L2298.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2298.03,1720.96 2298.03,1720.96 2298.32,1720.96 2298.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2298.32 1720.96 L2298.32 1720.96 L2298.6 1720.96 L2298.6 1720.96 L2298.32 1720.96 L2298.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2298.32,1720.96 2298.32,1720.96 2298.6,1720.96 2298.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2298.6 1720.96 L2298.6 1720.96 L2298.88 1720.96 L2298.88 1720.96 L2298.6 1720.96 L2298.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2298.6,1720.96 2298.6,1720.96 2298.88,1720.96 2298.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2298.88 1720.96 L2298.88 1720.96 L2299.16 1720.96 L2299.16 1720.96 L2298.88 1720.96 L2298.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2298.88,1720.96 2298.88,1720.96 2299.16,1720.96 2298.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2299.16 1720.96 L2299.16 1720.96 L2299.44 1720.96 L2299.44 1720.96 L2299.16 1720.96 L2299.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2299.16,1720.96 2299.16,1720.96 2299.44,1720.96 2299.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2299.44 1720.96 L2299.44 1720.96 L2299.72 1720.96 L2299.72 1720.96 L2299.44 1720.96 L2299.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2299.44,1720.96 2299.44,1720.96 2299.72,1720.96 2299.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2299.72 1720.96 L2299.72 1720.96 L2300.01 1720.96 L2300.01 1720.96 L2299.72 1720.96 L2299.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2299.72,1720.96 2299.72,1720.96 2300.01,1720.96 2299.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2300.01 1720.96 L2300.01 1720.96 L2300.29 1720.96 L2300.29 1720.96 L2300.01 1720.96 L2300.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2300.01,1720.96 2300.01,1720.96 2300.29,1720.96 2300.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2300.29 1720.96 L2300.29 1720.96 L2300.57 1720.96 L2300.57 1720.96 L2300.29 1720.96 L2300.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2300.29,1720.96 2300.29,1720.96 2300.57,1720.96 2300.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2300.57 1720.96 L2300.57 1720.96 L2300.85 1720.96 L2300.85 1720.96 L2300.57 1720.96 L2300.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2300.57,1720.96 2300.57,1720.96 2300.85,1720.96 2300.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2300.85 1720.96 L2300.85 1720.96 L2301.13 1720.96 L2301.13 1720.96 L2300.85 1720.96 L2300.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2300.85,1720.96 2300.85,1720.96 2301.13,1720.96 2300.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2301.13 1720.96 L2301.13 1720.96 L2301.41 1720.96 L2301.41 1720.96 L2301.13 1720.96 L2301.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2301.13,1720.96 2301.13,1720.96 2301.41,1720.96 2301.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2301.41 1720.96 L2301.41 1720.96 L2301.7 1720.96 L2301.7 1720.96 L2301.41 1720.96 L2301.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2301.41,1720.96 2301.41,1720.96 2301.7,1720.96 2301.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2301.7 1720.96 L2301.7 1720.96 L2301.98 1720.96 L2301.98 1720.96 L2301.7 1720.96 L2301.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2301.7,1720.96 2301.7,1720.96 2301.98,1720.96 2301.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2301.98 1720.96 L2301.98 1720.96 L2302.26 1720.96 L2302.26 1720.96 L2301.98 1720.96 L2301.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2301.98,1720.96 2301.98,1720.96 2302.26,1720.96 2301.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2302.26 1720.96 L2302.26 1720.96 L2302.54 1720.96 L2302.54 1720.96 L2302.26 1720.96 L2302.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2302.26,1720.96 2302.26,1720.96 2302.54,1720.96 2302.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2302.54 1720.96 L2302.54 1720.96 L2302.82 1720.96 L2302.82 1720.96 L2302.54 1720.96 L2302.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2302.54,1720.96 2302.54,1720.96 2302.82,1720.96 2302.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2302.82 1720.96 L2302.82 1720.96 L2303.1 1720.96 L2303.1 1720.96 L2302.82 1720.96 L2302.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2302.82,1720.96 2302.82,1720.96 2303.1,1720.96 2302.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2303.1 1720.96 L2303.1 1720.96 L2303.39 1720.96 L2303.39 1720.96 L2303.1 1720.96 L2303.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2303.1,1720.96 2303.1,1720.96 2303.39,1720.96 2303.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2303.39 1720.96 L2303.39 1720.96 L2303.67 1720.96 L2303.67 1720.96 L2303.39 1720.96 L2303.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2303.39,1720.96 2303.39,1720.96 2303.67,1720.96 2303.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2303.67 1720.96 L2303.67 1720.96 L2303.95 1720.96 L2303.95 1720.96 L2303.67 1720.96 L2303.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2303.67,1720.96 2303.67,1720.96 2303.95,1720.96 2303.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2303.95 1720.96 L2303.95 1720.96 L2304.23 1720.96 L2304.23 1720.96 L2303.95 1720.96 L2303.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2303.95,1720.96 2303.95,1720.96 2304.23,1720.96 2303.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2304.23 1720.96 L2304.23 1720.96 L2304.51 1720.96 L2304.51 1720.96 L2304.23 1720.96 L2304.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2304.23,1720.96 2304.23,1720.96 2304.51,1720.96 2304.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2304.51 1720.96 L2304.51 1720.96 L2304.79 1720.96 L2304.79 1720.96 L2304.51 1720.96 L2304.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2304.51,1720.96 2304.51,1720.96 2304.79,1720.96 2304.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2304.79 1720.96 L2304.79 1720.96 L2305.08 1720.96 L2305.08 1720.96 L2304.79 1720.96 L2304.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2304.79,1720.96 2304.79,1720.96 2305.08,1720.96 2304.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2305.08 1720.96 L2305.08 1720.96 L2305.36 1720.96 L2305.36 1720.96 L2305.08 1720.96 L2305.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2305.08,1720.96 2305.08,1720.96 2305.36,1720.96 2305.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2305.36 1720.96 L2305.36 1720.96 L2305.64 1720.96 L2305.64 1720.96 L2305.36 1720.96 L2305.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2305.36,1720.96 2305.36,1720.96 2305.64,1720.96 2305.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2305.64 1720.96 L2305.64 1720.96 L2305.92 1720.96 L2305.92 1720.96 L2305.64 1720.96 L2305.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2305.64,1720.96 2305.64,1720.96 2305.92,1720.96 2305.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2305.92 1720.96 L2305.92 1720.96 L2306.2 1720.96 L2306.2 1720.96 L2305.92 1720.96 L2305.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2305.92,1720.96 2305.92,1720.96 2306.2,1720.96 2305.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2306.2 1720.96 L2306.2 1720.96 L2306.49 1720.96 L2306.49 1720.96 L2306.2 1720.96 L2306.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2306.2,1720.96 2306.2,1720.96 2306.49,1720.96 2306.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2306.49 1720.96 L2306.49 1720.96 L2306.77 1720.96 L2306.77 1720.96 L2306.49 1720.96 L2306.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2306.49,1720.96 2306.49,1720.96 2306.77,1720.96 2306.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2306.77 1720.96 L2306.77 1720.96 L2307.05 1720.96 L2307.05 1720.96 L2306.77 1720.96 L2306.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2306.77,1720.96 2306.77,1720.96 2307.05,1720.96 2306.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2307.05 1720.96 L2307.05 1720.96 L2307.33 1720.96 L2307.33 1720.96 L2307.05 1720.96 L2307.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2307.05,1720.96 2307.05,1720.96 2307.33,1720.96 2307.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2307.33 1720.96 L2307.33 1720.96 L2307.61 1720.96 L2307.61 1720.96 L2307.33 1720.96 L2307.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2307.33,1720.96 2307.33,1720.96 2307.61,1720.96 2307.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2307.61 1720.96 L2307.61 1720.96 L2307.89 1720.96 L2307.89 1720.96 L2307.61 1720.96 L2307.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2307.61,1720.96 2307.61,1720.96 2307.89,1720.96 2307.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2307.89 1720.96 L2307.89 1720.96 L2308.18 1720.96 L2308.18 1720.96 L2307.89 1720.96 L2307.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2307.89,1720.96 2307.89,1720.96 2308.18,1720.96 2307.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2308.18 1720.96 L2308.18 1720.96 L2308.46 1720.96 L2308.46 1720.96 L2308.18 1720.96 L2308.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2308.18,1720.96 2308.18,1720.96 2308.46,1720.96 2308.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2308.46 1720.96 L2308.46 1720.96 L2308.74 1720.96 L2308.74 1720.96 L2308.46 1720.96 L2308.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2308.46,1720.96 2308.46,1720.96 2308.74,1720.96 2308.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2308.74 1720.96 L2308.74 1720.96 L2309.02 1720.96 L2309.02 1720.96 L2308.74 1720.96 L2308.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2308.74,1720.96 2308.74,1720.96 2309.02,1720.96 2308.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2309.02 1720.96 L2309.02 1720.96 L2309.3 1720.96 L2309.3 1720.96 L2309.02 1720.96 L2309.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2309.02,1720.96 2309.02,1720.96 2309.3,1720.96 2309.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2309.3 1720.96 L2309.3 1720.96 L2309.58 1720.96 L2309.58 1720.96 L2309.3 1720.96 L2309.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2309.3,1720.96 2309.3,1720.96 2309.58,1720.96 2309.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2309.58 1720.96 L2309.58 1720.96 L2309.87 1720.96 L2309.87 1720.96 L2309.58 1720.96 L2309.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2309.58,1720.96 2309.58,1720.96 2309.87,1720.96 2309.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2309.87 1720.96 L2309.87 1720.96 L2310.15 1720.96 L2310.15 1720.96 L2309.87 1720.96 L2309.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2309.87,1720.96 2309.87,1720.96 2310.15,1720.96 2309.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2310.15 1720.96 L2310.15 1720.96 L2310.43 1720.96 L2310.43 1720.96 L2310.15 1720.96 L2310.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2310.15,1720.96 2310.15,1720.96 2310.43,1720.96 2310.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2310.43 1720.96 L2310.43 1720.96 L2310.71 1720.96 L2310.71 1720.96 L2310.43 1720.96 L2310.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2310.43,1720.96 2310.43,1720.96 2310.71,1720.96 2310.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2310.71 1720.96 L2310.71 1720.96 L2310.99 1720.96 L2310.99 1720.96 L2310.71 1720.96 L2310.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2310.71,1720.96 2310.71,1720.96 2310.99,1720.96 2310.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2310.99 1720.96 L2310.99 1720.96 L2311.27 1720.96 L2311.27 1720.96 L2310.99 1720.96 L2310.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2310.99,1720.96 2310.99,1720.96 2311.27,1720.96 2310.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2311.27 1720.96 L2311.27 1720.96 L2311.56 1720.96 L2311.56 1720.96 L2311.27 1720.96 L2311.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2311.27,1720.96 2311.27,1720.96 2311.56,1720.96 2311.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2311.56 1720.96 L2311.56 1720.96 L2311.84 1720.96 L2311.84 1720.96 L2311.56 1720.96 L2311.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2311.56,1720.96 2311.56,1720.96 2311.84,1720.96 2311.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2311.84 1720.96 L2311.84 1720.96 L2312.12 1720.96 L2312.12 1720.96 L2311.84 1720.96 L2311.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2311.84,1720.96 2311.84,1720.96 2312.12,1720.96 2311.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2312.12 1720.96 L2312.12 1720.96 L2312.4 1720.96 L2312.4 1720.96 L2312.12 1720.96 L2312.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2312.12,1720.96 2312.12,1720.96 2312.4,1720.96 2312.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2312.4 1720.96 L2312.4 1720.96 L2312.68 1720.96 L2312.68 1720.96 L2312.4 1720.96 L2312.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2312.4,1720.96 2312.4,1720.96 2312.68,1720.96 2312.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2312.68 1720.96 L2312.68 1720.96 L2312.97 1720.96 L2312.97 1720.96 L2312.68 1720.96 L2312.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2312.68,1720.96 2312.68,1720.96 2312.97,1720.96 2312.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2312.97 1720.96 L2312.97 1720.96 L2313.25 1720.96 L2313.25 1720.96 L2312.97 1720.96 L2312.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2312.97,1720.96 2312.97,1720.96 2313.25,1720.96 2312.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2313.25 1720.96 L2313.25 1720.96 L2313.53 1720.96 L2313.53 1720.96 L2313.25 1720.96 L2313.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2313.25,1720.96 2313.25,1720.96 2313.53,1720.96 2313.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2313.53 1720.96 L2313.53 1720.96 L2313.81 1720.96 L2313.81 1720.96 L2313.53 1720.96 L2313.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2313.53,1720.96 2313.53,1720.96 2313.81,1720.96 2313.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2313.81 1720.96 L2313.81 1720.96 L2314.09 1720.96 L2314.09 1720.96 L2313.81 1720.96 L2313.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2313.81,1720.96 2313.81,1720.96 2314.09,1720.96 2313.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2314.09 1720.96 L2314.09 1720.96 L2314.37 1720.96 L2314.37 1720.96 L2314.09 1720.96 L2314.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2314.09,1720.96 2314.09,1720.96 2314.37,1720.96 2314.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2314.37 1720.96 L2314.37 1720.96 L2314.66 1720.96 L2314.66 1720.96 L2314.37 1720.96 L2314.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2314.37,1720.96 2314.37,1720.96 2314.66,1720.96 2314.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2314.66 1720.96 L2314.66 1720.96 L2314.94 1720.96 L2314.94 1720.96 L2314.66 1720.96 L2314.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2314.66,1720.96 2314.66,1720.96 2314.94,1720.96 2314.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2314.94 1720.96 L2314.94 1720.96 L2315.22 1720.96 L2315.22 1720.96 L2314.94 1720.96 L2314.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2314.94,1720.96 2314.94,1720.96 2315.22,1720.96 2314.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2315.22 1720.96 L2315.22 1720.96 L2315.5 1720.96 L2315.5 1720.96 L2315.22 1720.96 L2315.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2315.22,1720.96 2315.22,1720.96 2315.5,1720.96 2315.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2315.5 1720.96 L2315.5 1720.96 L2315.78 1720.96 L2315.78 1720.96 L2315.5 1720.96 L2315.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2315.5,1720.96 2315.5,1720.96 2315.78,1720.96 2315.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2315.78 1720.96 L2315.78 1720.96 L2316.06 1720.96 L2316.06 1720.96 L2315.78 1720.96 L2315.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2315.78,1720.96 2315.78,1720.96 2316.06,1720.96 2315.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2316.06 1720.96 L2316.06 1720.96 L2316.35 1720.96 L2316.35 1720.96 L2316.06 1720.96 L2316.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2316.06,1720.96 2316.06,1720.96 2316.35,1720.96 2316.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2316.35 1720.96 L2316.35 1720.96 L2316.63 1720.96 L2316.63 1720.96 L2316.35 1720.96 L2316.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2316.35,1720.96 2316.35,1720.96 2316.63,1720.96 2316.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2316.63 1720.96 L2316.63 1720.96 L2316.91 1720.96 L2316.91 1720.96 L2316.63 1720.96 L2316.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2316.63,1720.96 2316.63,1720.96 2316.91,1720.96 2316.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2316.91 1720.96 L2316.91 1720.96 L2317.19 1720.96 L2317.19 1720.96 L2316.91 1720.96 L2316.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2316.91,1720.96 2316.91,1720.96 2317.19,1720.96 2316.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2317.19 1720.96 L2317.19 1720.96 L2317.47 1720.96 L2317.47 1720.96 L2317.19 1720.96 L2317.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2317.19,1720.96 2317.19,1720.96 2317.47,1720.96 2317.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2317.47 1720.96 L2317.47 1720.96 L2317.75 1720.96 L2317.75 1720.96 L2317.47 1720.96 L2317.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2317.47,1720.96 2317.47,1720.96 2317.75,1720.96 2317.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2317.75 1720.96 L2317.75 1720.96 L2318.04 1720.96 L2318.04 1720.96 L2317.75 1720.96 L2317.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2317.75,1720.96 2317.75,1720.96 2318.04,1720.96 2317.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2318.04 1720.96 L2318.04 1720.96 L2318.32 1720.96 L2318.32 1720.96 L2318.04 1720.96 L2318.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2318.04,1720.96 2318.04,1720.96 2318.32,1720.96 2318.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2318.32 1720.96 L2318.32 1720.96 L2318.6 1720.96 L2318.6 1720.96 L2318.32 1720.96 L2318.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2318.32,1720.96 2318.32,1720.96 2318.6,1720.96 2318.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2318.6 1720.96 L2318.6 1720.96 L2318.88 1720.96 L2318.88 1720.96 L2318.6 1720.96 L2318.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2318.6,1720.96 2318.6,1720.96 2318.88,1720.96 2318.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2318.88 1720.96 L2318.88 1720.96 L2319.16 1720.96 L2319.16 1720.96 L2318.88 1720.96 L2318.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2318.88,1720.96 2318.88,1720.96 2319.16,1720.96 2318.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2319.16 1720.96 L2319.16 1720.96 L2319.44 1720.96 L2319.44 1720.96 L2319.16 1720.96 L2319.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2319.16,1720.96 2319.16,1720.96 2319.44,1720.96 2319.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2319.44 1720.96 L2319.44 1720.96 L2319.73 1720.96 L2319.73 1720.96 L2319.44 1720.96 L2319.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2319.44,1720.96 2319.44,1720.96 2319.73,1720.96 2319.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2319.73 1720.96 L2319.73 1720.96 L2320.01 1720.96 L2320.01 1720.96 L2319.73 1720.96 L2319.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2319.73,1720.96 2319.73,1720.96 2320.01,1720.96 2319.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2320.01 1720.96 L2320.01 1720.96 L2320.29 1720.96 L2320.29 1720.96 L2320.01 1720.96 L2320.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2320.01,1720.96 2320.01,1720.96 2320.29,1720.96 2320.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2320.29 1720.96 L2320.29 1720.96 L2320.57 1720.96 L2320.57 1720.96 L2320.29 1720.96 L2320.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2320.29,1720.96 2320.29,1720.96 2320.57,1720.96 2320.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2320.57 1720.96 L2320.57 1720.96 L2320.85 1720.96 L2320.85 1720.96 L2320.57 1720.96 L2320.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2320.57,1720.96 2320.57,1720.96 2320.85,1720.96 2320.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2320.85 1720.96 L2320.85 1720.96 L2321.14 1720.96 L2321.14 1720.96 L2320.85 1720.96 L2320.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2320.85,1720.96 2320.85,1720.96 2321.14,1720.96 2320.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2321.14 1720.96 L2321.14 1720.96 L2321.42 1720.96 L2321.42 1720.96 L2321.14 1720.96 L2321.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2321.14,1720.96 2321.14,1720.96 2321.42,1720.96 2321.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2321.42 1720.96 L2321.42 1720.96 L2321.7 1720.96 L2321.7 1720.96 L2321.42 1720.96 L2321.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2321.42,1720.96 2321.42,1720.96 2321.7,1720.96 2321.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2321.7 1720.96 L2321.7 1720.96 L2321.98 1720.96 L2321.98 1720.96 L2321.7 1720.96 L2321.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2321.7,1720.96 2321.7,1720.96 2321.98,1720.96 2321.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2321.98 1720.96 L2321.98 1720.96 L2322.26 1720.96 L2322.26 1720.96 L2321.98 1720.96 L2321.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2321.98,1720.96 2321.98,1720.96 2322.26,1720.96 2321.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2322.26 1720.96 L2322.26 1720.96 L2322.54 1720.96 L2322.54 1720.96 L2322.26 1720.96 L2322.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2322.26,1720.96 2322.26,1720.96 2322.54,1720.96 2322.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2322.54 1720.96 L2322.54 1720.96 L2322.83 1720.96 L2322.83 1720.96 L2322.54 1720.96 L2322.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2322.54,1720.96 2322.54,1720.96 2322.83,1720.96 2322.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2322.83 1720.96 L2322.83 1720.96 L2323.11 1720.96 L2323.11 1720.96 L2322.83 1720.96 L2322.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2322.83,1720.96 2322.83,1720.96 2323.11,1720.96 2322.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2323.11 1720.96 L2323.11 1720.96 L2323.39 1720.96 L2323.39 1720.96 L2323.11 1720.96 L2323.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2323.11,1720.96 2323.11,1720.96 2323.39,1720.96 2323.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2323.39 1720.96 L2323.39 1720.96 L2323.67 1720.96 L2323.67 1720.96 L2323.39 1720.96 L2323.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2323.39,1720.96 2323.39,1720.96 2323.67,1720.96 2323.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2323.67 1720.96 L2323.67 1720.96 L2323.95 1720.96 L2323.95 1720.96 L2323.67 1720.96 L2323.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2323.67,1720.96 2323.67,1720.96 2323.95,1720.96 2323.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2323.95 1720.96 L2323.95 1720.96 L2324.23 1720.96 L2324.23 1720.96 L2323.95 1720.96 L2323.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2323.95,1720.96 2323.95,1720.96 2324.23,1720.96 2323.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2324.23 1720.96 L2324.23 1720.96 L2324.52 1720.96 L2324.52 1720.96 L2324.23 1720.96 L2324.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2324.23,1720.96 2324.23,1720.96 2324.52,1720.96 2324.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2324.52 1720.96 L2324.52 1720.96 L2324.8 1720.96 L2324.8 1720.96 L2324.52 1720.96 L2324.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2324.52,1720.96 2324.52,1720.96 2324.8,1720.96 2324.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2324.8 1720.96 L2324.8 1720.96 L2325.08 1720.96 L2325.08 1720.96 L2324.8 1720.96 L2324.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2324.8,1720.96 2324.8,1720.96 2325.08,1720.96 2324.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2325.08 1720.96 L2325.08 1720.96 L2325.36 1720.96 L2325.36 1720.96 L2325.08 1720.96 L2325.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2325.08,1720.96 2325.08,1720.96 2325.36,1720.96 2325.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2325.36 1720.96 L2325.36 1720.96 L2325.64 1720.96 L2325.64 1720.96 L2325.36 1720.96 L2325.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2325.36,1720.96 2325.36,1720.96 2325.64,1720.96 2325.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2325.64 1720.96 L2325.64 1720.96 L2325.92 1720.96 L2325.92 1720.96 L2325.64 1720.96 L2325.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2325.64,1720.96 2325.64,1720.96 2325.92,1720.96 2325.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2325.92 1720.96 L2325.92 1720.96 L2326.21 1720.96 L2326.21 1720.96 L2325.92 1720.96 L2325.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2325.92,1720.96 2325.92,1720.96 2326.21,1720.96 2325.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2326.21 1720.96 L2326.21 1720.96 L2326.49 1720.96 L2326.49 1720.96 L2326.21 1720.96 L2326.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2326.21,1720.96 2326.21,1720.96 2326.49,1720.96 2326.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2326.49 1720.96 L2326.49 1720.96 L2326.77 1720.96 L2326.77 1720.96 L2326.49 1720.96 L2326.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2326.49,1720.96 2326.49,1720.96 2326.77,1720.96 2326.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2326.77 1720.96 L2326.77 1720.96 L2327.05 1720.96 L2327.05 1720.96 L2326.77 1720.96 L2326.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2326.77,1720.96 2326.77,1720.96 2327.05,1720.96 2326.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2327.05 1720.96 L2327.05 1720.96 L2327.33 1720.96 L2327.33 1720.96 L2327.05 1720.96 L2327.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2327.05,1720.96 2327.05,1720.96 2327.33,1720.96 2327.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2327.33 1720.96 L2327.33 1720.96 L2327.61 1720.96 L2327.61 1720.96 L2327.33 1720.96 L2327.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2327.33,1720.96 2327.33,1720.96 2327.61,1720.96 2327.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2327.61 1720.96 L2327.61 1720.96 L2327.9 1720.96 L2327.9 1720.96 L2327.61 1720.96 L2327.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2327.61,1720.96 2327.61,1720.96 2327.9,1720.96 2327.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2327.9 1720.96 L2327.9 1720.96 L2328.18 1720.96 L2328.18 1720.96 L2327.9 1720.96 L2327.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2327.9,1720.96 2327.9,1720.96 2328.18,1720.96 2327.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2328.18 1720.96 L2328.18 1720.96 L2328.46 1720.96 L2328.46 1720.96 L2328.18 1720.96 L2328.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2328.18,1720.96 2328.18,1720.96 2328.46,1720.96 2328.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2328.46 1720.96 L2328.46 1720.96 L2328.74 1720.96 L2328.74 1720.96 L2328.46 1720.96 L2328.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2328.46,1720.96 2328.46,1720.96 2328.74,1720.96 2328.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2328.74 1720.96 L2328.74 1720.96 L2329.02 1720.96 L2329.02 1720.96 L2328.74 1720.96 L2328.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2328.74,1720.96 2328.74,1720.96 2329.02,1720.96 2328.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2329.02 1720.96 L2329.02 1720.96 L2329.31 1720.96 L2329.31 1720.96 L2329.02 1720.96 L2329.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2329.02,1720.96 2329.02,1720.96 2329.31,1720.96 2329.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2329.31 1720.96 L2329.31 1720.96 L2329.59 1720.96 L2329.59 1720.96 L2329.31 1720.96 L2329.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2329.31,1720.96 2329.31,1720.96 2329.59,1720.96 2329.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2329.59 1720.96 L2329.59 1720.96 L2329.87 1720.96 L2329.87 1720.96 L2329.59 1720.96 L2329.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2329.59,1720.96 2329.59,1720.96 2329.87,1720.96 2329.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2329.87 1720.96 L2329.87 1720.96 L2330.15 1720.96 L2330.15 1720.96 L2329.87 1720.96 L2329.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2329.87,1720.96 2329.87,1720.96 2330.15,1720.96 2329.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2330.15 1720.96 L2330.15 1720.96 L2330.43 1720.96 L2330.43 1720.96 L2330.15 1720.96 L2330.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2330.15,1720.96 2330.15,1720.96 2330.43,1720.96 2330.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2330.43 1720.96 L2330.43 1720.96 L2330.71 1720.96 L2330.71 1720.96 L2330.43 1720.96 L2330.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2330.43,1720.96 2330.43,1720.96 2330.71,1720.96 2330.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2330.71 1720.96 L2330.71 1720.96 L2331 1720.96 L2331 1720.96 L2330.71 1720.96 L2330.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2330.71,1720.96 2330.71,1720.96 2331,1720.96 2330.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2331 1720.96 L2331 1720.96 L2331.28 1720.96 L2331.28 1720.96 L2331 1720.96 L2331 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2331,1720.96 2331,1720.96 2331.28,1720.96 2331,1720.96 "/>
<path clip-path="url(#clip322)" d="M2331.28 1720.96 L2331.28 1720.96 L2331.56 1720.96 L2331.56 1720.96 L2331.28 1720.96 L2331.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2331.28,1720.96 2331.28,1720.96 2331.56,1720.96 2331.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2331.56 1720.96 L2331.56 1720.96 L2331.84 1720.96 L2331.84 1720.96 L2331.56 1720.96 L2331.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2331.56,1720.96 2331.56,1720.96 2331.84,1720.96 2331.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2331.84 1720.96 L2331.84 1720.96 L2332.12 1720.96 L2332.12 1720.96 L2331.84 1720.96 L2331.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2331.84,1720.96 2331.84,1720.96 2332.12,1720.96 2331.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2332.12 1720.96 L2332.12 1720.96 L2332.4 1720.96 L2332.4 1720.96 L2332.12 1720.96 L2332.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2332.12,1720.96 2332.12,1720.96 2332.4,1720.96 2332.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2332.4 1720.96 L2332.4 1720.96 L2332.69 1720.96 L2332.69 1720.96 L2332.4 1720.96 L2332.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2332.4,1720.96 2332.4,1720.96 2332.69,1720.96 2332.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2332.69 1720.96 L2332.69 1720.96 L2332.97 1720.96 L2332.97 1720.96 L2332.69 1720.96 L2332.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2332.69,1720.96 2332.69,1720.96 2332.97,1720.96 2332.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2332.97 1720.96 L2332.97 1720.96 L2333.25 1720.96 L2333.25 1720.96 L2332.97 1720.96 L2332.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2332.97,1720.96 2332.97,1720.96 2333.25,1720.96 2332.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2333.25 1720.96 L2333.25 1720.96 L2333.53 1720.96 L2333.53 1720.96 L2333.25 1720.96 L2333.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2333.25,1720.96 2333.25,1720.96 2333.53,1720.96 2333.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2333.53 1720.96 L2333.53 1720.96 L2333.81 1720.96 L2333.81 1720.96 L2333.53 1720.96 L2333.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2333.53,1720.96 2333.53,1720.96 2333.81,1720.96 2333.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2333.81 1720.96 L2333.81 1720.96 L2334.09 1720.96 L2334.09 1720.96 L2333.81 1720.96 L2333.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2333.81,1720.96 2333.81,1720.96 2334.09,1720.96 2333.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2334.09 1720.96 L2334.09 1720.96 L2334.38 1720.96 L2334.38 1720.96 L2334.09 1720.96 L2334.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2334.09,1720.96 2334.09,1720.96 2334.38,1720.96 2334.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2334.38 1720.96 L2334.38 1720.96 L2334.66 1720.96 L2334.66 1720.96 L2334.38 1720.96 L2334.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2334.38,1720.96 2334.38,1720.96 2334.66,1720.96 2334.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2334.66 1720.96 L2334.66 1720.96 L2334.94 1720.96 L2334.94 1720.96 L2334.66 1720.96 L2334.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2334.66,1720.96 2334.66,1720.96 2334.94,1720.96 2334.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2334.94 1720.96 L2334.94 1720.96 L2335.22 1720.96 L2335.22 1720.96 L2334.94 1720.96 L2334.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2334.94,1720.96 2334.94,1720.96 2335.22,1720.96 2334.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2335.22 1720.96 L2335.22 1720.96 L2335.5 1720.96 L2335.5 1720.96 L2335.22 1720.96 L2335.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2335.22,1720.96 2335.22,1720.96 2335.5,1720.96 2335.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2335.5 1720.96 L2335.5 1720.96 L2335.78 1720.96 L2335.78 1720.96 L2335.5 1720.96 L2335.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2335.5,1720.96 2335.5,1720.96 2335.78,1720.96 2335.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2335.78 1720.96 L2335.78 1720.96 L2336.07 1720.96 L2336.07 1720.96 L2335.78 1720.96 L2335.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2335.78,1720.96 2335.78,1720.96 2336.07,1720.96 2335.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2336.07 1720.96 L2336.07 1720.96 L2336.35 1720.96 L2336.35 1720.96 L2336.07 1720.96 L2336.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2336.07,1720.96 2336.07,1720.96 2336.35,1720.96 2336.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2336.35 1720.96 L2336.35 1720.96 L2336.63 1720.96 L2336.63 1720.96 L2336.35 1720.96 L2336.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2336.35,1720.96 2336.35,1720.96 2336.63,1720.96 2336.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2336.63 1720.96 L2336.63 1720.96 L2336.91 1720.96 L2336.91 1720.96 L2336.63 1720.96 L2336.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2336.63,1720.96 2336.63,1720.96 2336.91,1720.96 2336.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2336.91 1720.96 L2336.91 1720.96 L2337.19 1720.96 L2337.19 1720.96 L2336.91 1720.96 L2336.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2336.91,1720.96 2336.91,1720.96 2337.19,1720.96 2336.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2337.19 1720.96 L2337.19 1720.96 L2337.48 1720.96 L2337.48 1720.96 L2337.19 1720.96 L2337.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2337.19,1720.96 2337.19,1720.96 2337.48,1720.96 2337.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2337.48 1720.96 L2337.48 1720.96 L2337.76 1720.96 L2337.76 1720.96 L2337.48 1720.96 L2337.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2337.48,1720.96 2337.48,1720.96 2337.76,1720.96 2337.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2337.76 1720.96 L2337.76 1720.96 L2338.04 1720.96 L2338.04 1720.96 L2337.76 1720.96 L2337.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2337.76,1720.96 2337.76,1720.96 2338.04,1720.96 2337.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2338.04 1720.96 L2338.04 1720.96 L2338.32 1720.96 L2338.32 1720.96 L2338.04 1720.96 L2338.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2338.04,1720.96 2338.04,1720.96 2338.32,1720.96 2338.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2338.32 1720.96 L2338.32 1720.96 L2338.6 1720.96 L2338.6 1720.96 L2338.32 1720.96 L2338.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2338.32,1720.96 2338.32,1720.96 2338.6,1720.96 2338.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2338.6 1720.96 L2338.6 1720.96 L2338.88 1720.96 L2338.88 1720.96 L2338.6 1720.96 L2338.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2338.6,1720.96 2338.6,1720.96 2338.88,1720.96 2338.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2338.88 1720.96 L2338.88 1720.96 L2339.17 1720.96 L2339.17 1720.96 L2338.88 1720.96 L2338.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2338.88,1720.96 2338.88,1720.96 2339.17,1720.96 2338.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2339.17 1720.96 L2339.17 1720.96 L2339.45 1720.96 L2339.45 1720.96 L2339.17 1720.96 L2339.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2339.17,1720.96 2339.17,1720.96 2339.45,1720.96 2339.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2339.45 1720.96 L2339.45 1720.96 L2339.73 1720.96 L2339.73 1720.96 L2339.45 1720.96 L2339.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2339.45,1720.96 2339.45,1720.96 2339.73,1720.96 2339.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2339.73 1720.96 L2339.73 1720.96 L2340.01 1720.96 L2340.01 1720.96 L2339.73 1720.96 L2339.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2339.73,1720.96 2339.73,1720.96 2340.01,1720.96 2339.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2340.01 1720.96 L2340.01 1720.96 L2340.29 1720.96 L2340.29 1720.96 L2340.01 1720.96 L2340.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2340.01,1720.96 2340.01,1720.96 2340.29,1720.96 2340.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2340.29 1720.96 L2340.29 1720.96 L2340.57 1720.96 L2340.57 1720.96 L2340.29 1720.96 L2340.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2340.29,1720.96 2340.29,1720.96 2340.57,1720.96 2340.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2340.57 1720.96 L2340.57 1720.96 L2340.86 1720.96 L2340.86 1720.96 L2340.57 1720.96 L2340.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2340.57,1720.96 2340.57,1720.96 2340.86,1720.96 2340.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2340.86 1720.96 L2340.86 1720.96 L2341.14 1720.96 L2341.14 1720.96 L2340.86 1720.96 L2340.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2340.86,1720.96 2340.86,1720.96 2341.14,1720.96 2340.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2341.14 1720.96 L2341.14 1720.96 L2341.42 1720.96 L2341.42 1720.96 L2341.14 1720.96 L2341.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2341.14,1720.96 2341.14,1720.96 2341.42,1720.96 2341.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2341.42 1720.96 L2341.42 1720.96 L2341.7 1720.96 L2341.7 1720.96 L2341.42 1720.96 L2341.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2341.42,1720.96 2341.42,1720.96 2341.7,1720.96 2341.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2341.7 1720.96 L2341.7 1720.96 L2341.98 1720.96 L2341.98 1720.96 L2341.7 1720.96 L2341.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2341.7,1720.96 2341.7,1720.96 2341.98,1720.96 2341.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2341.98 1720.96 L2341.98 1720.96 L2342.26 1720.96 L2342.26 1720.96 L2341.98 1720.96 L2341.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2341.98,1720.96 2341.98,1720.96 2342.26,1720.96 2341.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2342.26 1720.96 L2342.26 1720.96 L2342.55 1720.96 L2342.55 1720.96 L2342.26 1720.96 L2342.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2342.26,1720.96 2342.26,1720.96 2342.55,1720.96 2342.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2342.55 1720.96 L2342.55 1720.96 L2342.83 1720.96 L2342.83 1720.96 L2342.55 1720.96 L2342.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2342.55,1720.96 2342.55,1720.96 2342.83,1720.96 2342.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2342.83 1720.96 L2342.83 1720.96 L2343.11 1720.96 L2343.11 1720.96 L2342.83 1720.96 L2342.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2342.83,1720.96 2342.83,1720.96 2343.11,1720.96 2342.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2343.11 1720.96 L2343.11 1720.96 L2343.39 1720.96 L2343.39 1720.96 L2343.11 1720.96 L2343.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2343.11,1720.96 2343.11,1720.96 2343.39,1720.96 2343.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2343.39 1720.96 L2343.39 1720.96 L2343.67 1720.96 L2343.67 1720.96 L2343.39 1720.96 L2343.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2343.39,1720.96 2343.39,1720.96 2343.67,1720.96 2343.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2343.67 1720.96 L2343.67 1720.96 L2343.95 1720.96 L2343.95 1720.96 L2343.67 1720.96 L2343.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2343.67,1720.96 2343.67,1720.96 2343.95,1720.96 2343.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2343.95 1720.96 L2343.95 1720.96 L2344.24 1720.96 L2344.24 1720.96 L2343.95 1720.96 L2343.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2343.95,1720.96 2343.95,1720.96 2344.24,1720.96 2343.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2344.24 1720.96 L2344.24 1720.96 L2344.52 1720.96 L2344.52 1720.96 L2344.24 1720.96 L2344.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2344.24,1720.96 2344.24,1720.96 2344.52,1720.96 2344.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2344.52 1720.96 L2344.52 1720.96 L2344.8 1720.96 L2344.8 1720.96 L2344.52 1720.96 L2344.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2344.52,1720.96 2344.52,1720.96 2344.8,1720.96 2344.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2344.8 1720.96 L2344.8 1720.96 L2345.08 1720.96 L2345.08 1720.96 L2344.8 1720.96 L2344.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2344.8,1720.96 2344.8,1720.96 2345.08,1720.96 2344.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2345.08 1720.96 L2345.08 1720.96 L2345.36 1720.96 L2345.36 1720.96 L2345.08 1720.96 L2345.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2345.08,1720.96 2345.08,1720.96 2345.36,1720.96 2345.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2345.36 1720.96 L2345.36 1720.96 L2345.65 1720.96 L2345.65 1720.96 L2345.36 1720.96 L2345.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2345.36,1720.96 2345.36,1720.96 2345.65,1720.96 2345.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2345.65 1720.96 L2345.65 1720.96 L2345.93 1720.96 L2345.93 1720.96 L2345.65 1720.96 L2345.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2345.65,1720.96 2345.65,1720.96 2345.93,1720.96 2345.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2345.93 1720.96 L2345.93 1720.96 L2346.21 1720.96 L2346.21 1720.96 L2345.93 1720.96 L2345.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2345.93,1720.96 2345.93,1720.96 2346.21,1720.96 2345.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2346.21 1720.96 L2346.21 1720.96 L2346.49 1720.96 L2346.49 1720.96 L2346.21 1720.96 L2346.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2346.21,1720.96 2346.21,1720.96 2346.49,1720.96 2346.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2346.49 1720.96 L2346.49 1720.96 L2346.77 1720.96 L2346.77 1720.96 L2346.49 1720.96 L2346.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2346.49,1720.96 2346.49,1720.96 2346.77,1720.96 2346.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2346.77 1720.96 L2346.77 1720.96 L2347.05 1720.96 L2347.05 1720.96 L2346.77 1720.96 L2346.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2346.77,1720.96 2346.77,1720.96 2347.05,1720.96 2346.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2347.05 1720.96 L2347.05 1720.96 L2347.34 1720.96 L2347.34 1720.96 L2347.05 1720.96 L2347.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2347.05,1720.96 2347.05,1720.96 2347.34,1720.96 2347.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2347.34 1720.96 L2347.34 1720.96 L2347.62 1720.96 L2347.62 1720.96 L2347.34 1720.96 L2347.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2347.34,1720.96 2347.34,1720.96 2347.62,1720.96 2347.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2347.62 1720.96 L2347.62 1720.96 L2347.9 1720.96 L2347.9 1720.96 L2347.62 1720.96 L2347.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2347.62,1720.96 2347.62,1720.96 2347.9,1720.96 2347.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2347.9 1720.96 L2347.9 1720.96 L2348.18 1720.96 L2348.18 1720.96 L2347.9 1720.96 L2347.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2347.9,1720.96 2347.9,1720.96 2348.18,1720.96 2347.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2348.18 1720.96 L2348.18 1720.96 L2348.46 1720.96 L2348.46 1720.96 L2348.18 1720.96 L2348.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2348.18,1720.96 2348.18,1720.96 2348.46,1720.96 2348.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2348.46 1720.96 L2348.46 1720.96 L2348.74 1720.96 L2348.74 1720.96 L2348.46 1720.96 L2348.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2348.46,1720.96 2348.46,1720.96 2348.74,1720.96 2348.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2348.74 1720.96 L2348.74 1720.96 L2349.03 1720.96 L2349.03 1720.96 L2348.74 1720.96 L2348.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2348.74,1720.96 2348.74,1720.96 2349.03,1720.96 2348.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2349.03 1720.96 L2349.03 1720.96 L2349.31 1720.96 L2349.31 1720.96 L2349.03 1720.96 L2349.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2349.03,1720.96 2349.03,1720.96 2349.31,1720.96 2349.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2349.31 1720.96 L2349.31 1720.96 L2349.59 1720.96 L2349.59 1720.96 L2349.31 1720.96 L2349.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2349.31,1720.96 2349.31,1720.96 2349.59,1720.96 2349.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2349.59 1720.96 L2349.59 1720.96 L2349.87 1720.96 L2349.87 1720.96 L2349.59 1720.96 L2349.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2349.59,1720.96 2349.59,1720.96 2349.87,1720.96 2349.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2349.87 1720.96 L2349.87 1720.96 L2350.15 1720.96 L2350.15 1720.96 L2349.87 1720.96 L2349.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2349.87,1720.96 2349.87,1720.96 2350.15,1720.96 2349.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2350.15 1720.96 L2350.15 1720.96 L2350.43 1720.96 L2350.43 1720.96 L2350.15 1720.96 L2350.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2350.15,1720.96 2350.15,1720.96 2350.43,1720.96 2350.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2350.43 1720.96 L2350.43 1720.96 L2350.72 1720.96 L2350.72 1720.96 L2350.43 1720.96 L2350.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2350.43,1720.96 2350.43,1720.96 2350.72,1720.96 2350.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2350.72 1720.96 L2350.72 1720.96 L2351 1720.96 L2351 1720.96 L2350.72 1720.96 L2350.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2350.72,1720.96 2350.72,1720.96 2351,1720.96 2350.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2351 1720.96 L2351 1720.96 L2351.28 1720.96 L2351.28 1720.96 L2351 1720.96 L2351 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2351,1720.96 2351,1720.96 2351.28,1720.96 2351,1720.96 "/>
<path clip-path="url(#clip322)" d="M2351.28 1720.96 L2351.28 1720.96 L2351.56 1720.96 L2351.56 1720.96 L2351.28 1720.96 L2351.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2351.28,1720.96 2351.28,1720.96 2351.56,1720.96 2351.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2351.56 1720.96 L2351.56 1720.96 L2351.84 1720.96 L2351.84 1720.96 L2351.56 1720.96 L2351.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2351.56,1720.96 2351.56,1720.96 2351.84,1720.96 2351.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2351.84 1720.96 L2351.84 1720.96 L2352.12 1720.96 L2352.12 1720.96 L2351.84 1720.96 L2351.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2351.84,1720.96 2351.84,1720.96 2352.12,1720.96 2351.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2352.12 1720.96 L2352.12 1720.96 L2352.41 1720.96 L2352.41 1720.96 L2352.12 1720.96 L2352.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2352.12,1720.96 2352.12,1720.96 2352.41,1720.96 2352.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2352.41 1720.96 L2352.41 1720.96 L2352.69 1720.96 L2352.69 1720.96 L2352.41 1720.96 L2352.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2352.41,1720.96 2352.41,1720.96 2352.69,1720.96 2352.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2352.69 1720.96 L2352.69 1720.96 L2352.97 1720.96 L2352.97 1720.96 L2352.69 1720.96 L2352.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2352.69,1720.96 2352.69,1720.96 2352.97,1720.96 2352.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2352.97 1720.96 L2352.97 1720.96 L2353.25 1720.96 L2353.25 1720.96 L2352.97 1720.96 L2352.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2352.97,1720.96 2352.97,1720.96 2353.25,1720.96 2352.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2353.25 1720.96 L2353.25 1720.96 L2353.53 1720.96 L2353.53 1720.96 L2353.25 1720.96 L2353.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2353.25,1720.96 2353.25,1720.96 2353.53,1720.96 2353.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2353.53 1720.96 L2353.53 1720.96 L2353.82 1720.96 L2353.82 1720.96 L2353.53 1720.96 L2353.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2353.53,1720.96 2353.53,1720.96 2353.82,1720.96 2353.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2353.82 1720.96 L2353.82 1720.96 L2354.1 1720.96 L2354.1 1720.96 L2353.82 1720.96 L2353.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2353.82,1720.96 2353.82,1720.96 2354.1,1720.96 2353.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2354.1 1720.96 L2354.1 1720.96 L2354.38 1720.96 L2354.38 1720.96 L2354.1 1720.96 L2354.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2354.1,1720.96 2354.1,1720.96 2354.38,1720.96 2354.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2354.38 1720.96 L2354.38 1720.96 L2354.66 1720.96 L2354.66 1720.96 L2354.38 1720.96 L2354.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2354.38,1720.96 2354.38,1720.96 2354.66,1720.96 2354.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2354.66 1720.96 L2354.66 1720.96 L2354.94 1720.96 L2354.94 1720.96 L2354.66 1720.96 L2354.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2354.66,1720.96 2354.66,1720.96 2354.94,1720.96 2354.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2354.94 1720.96 L2354.94 1720.96 L2355.22 1720.96 L2355.22 1720.96 L2354.94 1720.96 L2354.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2354.94,1720.96 2354.94,1720.96 2355.22,1720.96 2354.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2355.22 1720.96 L2355.22 1720.96 L2355.51 1720.96 L2355.51 1720.96 L2355.22 1720.96 L2355.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2355.22,1720.96 2355.22,1720.96 2355.51,1720.96 2355.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2355.51 1720.96 L2355.51 1720.96 L2355.79 1720.96 L2355.79 1720.96 L2355.51 1720.96 L2355.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2355.51,1720.96 2355.51,1720.96 2355.79,1720.96 2355.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2355.79 1720.96 L2355.79 1720.96 L2356.07 1720.96 L2356.07 1720.96 L2355.79 1720.96 L2355.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2355.79,1720.96 2355.79,1720.96 2356.07,1720.96 2355.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2356.07 1720.96 L2356.07 1720.96 L2356.35 1720.96 L2356.35 1720.96 L2356.07 1720.96 L2356.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2356.07,1720.96 2356.07,1720.96 2356.35,1720.96 2356.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2356.35 1720.96 L2356.35 1720.96 L2356.63 1720.96 L2356.63 1720.96 L2356.35 1720.96 L2356.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2356.35,1720.96 2356.35,1720.96 2356.63,1720.96 2356.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2356.63 1720.96 L2356.63 1720.96 L2356.91 1720.96 L2356.91 1720.96 L2356.63 1720.96 L2356.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2356.63,1720.96 2356.63,1720.96 2356.91,1720.96 2356.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2356.91 1720.96 L2356.91 1720.96 L2357.2 1720.96 L2357.2 1720.96 L2356.91 1720.96 L2356.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2356.91,1720.96 2356.91,1720.96 2357.2,1720.96 2356.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2357.2 1720.96 L2357.2 1720.96 L2357.48 1720.96 L2357.48 1720.96 L2357.2 1720.96 L2357.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2357.2,1720.96 2357.2,1720.96 2357.48,1720.96 2357.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2357.48 1720.96 L2357.48 1720.96 L2357.76 1720.96 L2357.76 1720.96 L2357.48 1720.96 L2357.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2357.48,1720.96 2357.48,1720.96 2357.76,1720.96 2357.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2357.76 1720.96 L2357.76 1720.96 L2358.04 1720.96 L2358.04 1720.96 L2357.76 1720.96 L2357.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2357.76,1720.96 2357.76,1720.96 2358.04,1720.96 2357.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2358.04 1720.96 L2358.04 1720.96 L2358.32 1720.96 L2358.32 1720.96 L2358.04 1720.96 L2358.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2358.04,1720.96 2358.04,1720.96 2358.32,1720.96 2358.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2358.32 1720.96 L2358.32 1720.96 L2358.6 1720.96 L2358.6 1720.96 L2358.32 1720.96 L2358.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2358.32,1720.96 2358.32,1720.96 2358.6,1720.96 2358.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2358.6 1720.96 L2358.6 1720.96 L2358.89 1720.96 L2358.89 1720.96 L2358.6 1720.96 L2358.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2358.6,1720.96 2358.6,1720.96 2358.89,1720.96 2358.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2358.89 1720.96 L2358.89 1720.96 L2359.17 1720.96 L2359.17 1720.96 L2358.89 1720.96 L2358.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2358.89,1720.96 2358.89,1720.96 2359.17,1720.96 2358.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2359.17 1720.96 L2359.17 1720.96 L2359.45 1720.96 L2359.45 1720.96 L2359.17 1720.96 L2359.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2359.17,1720.96 2359.17,1720.96 2359.45,1720.96 2359.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2359.45 1720.96 L2359.45 1720.96 L2359.73 1720.96 L2359.73 1720.96 L2359.45 1720.96 L2359.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2359.45,1720.96 2359.45,1720.96 2359.73,1720.96 2359.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2359.73 1720.96 L2359.73 1720.96 L2360.01 1720.96 L2360.01 1720.96 L2359.73 1720.96 L2359.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2359.73,1720.96 2359.73,1720.96 2360.01,1720.96 2359.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2360.01 1720.96 L2360.01 1720.96 L2360.29 1720.96 L2360.29 1720.96 L2360.01 1720.96 L2360.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2360.01,1720.96 2360.01,1720.96 2360.29,1720.96 2360.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2360.29 1720.96 L2360.29 1720.96 L2360.58 1720.96 L2360.58 1720.96 L2360.29 1720.96 L2360.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2360.29,1720.96 2360.29,1720.96 2360.58,1720.96 2360.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2360.58 1720.96 L2360.58 1720.96 L2360.86 1720.96 L2360.86 1720.96 L2360.58 1720.96 L2360.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2360.58,1720.96 2360.58,1720.96 2360.86,1720.96 2360.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2360.86 1720.96 L2360.86 1720.96 L2361.14 1720.96 L2361.14 1720.96 L2360.86 1720.96 L2360.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2360.86,1720.96 2360.86,1720.96 2361.14,1720.96 2360.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2361.14 1720.96 L2361.14 1720.96 L2361.42 1720.96 L2361.42 1720.96 L2361.14 1720.96 L2361.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2361.14,1720.96 2361.14,1720.96 2361.42,1720.96 2361.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2361.42 1720.96 L2361.42 1720.96 L2361.7 1720.96 L2361.7 1720.96 L2361.42 1720.96 L2361.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2361.42,1720.96 2361.42,1720.96 2361.7,1720.96 2361.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2361.7 1720.96 L2361.7 1720.96 L2361.99 1720.96 L2361.99 1720.96 L2361.7 1720.96 L2361.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2361.7,1720.96 2361.7,1720.96 2361.99,1720.96 2361.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2361.99 1720.96 L2361.99 1720.96 L2362.27 1720.96 L2362.27 1720.96 L2361.99 1720.96 L2361.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2361.99,1720.96 2361.99,1720.96 2362.27,1720.96 2361.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2362.27 1720.96 L2362.27 1720.96 L2362.55 1720.96 L2362.55 1720.96 L2362.27 1720.96 L2362.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2362.27,1720.96 2362.27,1720.96 2362.55,1720.96 2362.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2362.55 1720.96 L2362.55 1720.96 L2362.83 1720.96 L2362.83 1720.96 L2362.55 1720.96 L2362.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2362.55,1720.96 2362.55,1720.96 2362.83,1720.96 2362.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2362.83 1720.96 L2362.83 1720.96 L2363.11 1720.96 L2363.11 1720.96 L2362.83 1720.96 L2362.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2362.83,1720.96 2362.83,1720.96 2363.11,1720.96 2362.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2363.11 1720.96 L2363.11 1720.96 L2363.39 1720.96 L2363.39 1720.96 L2363.11 1720.96 L2363.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2363.11,1720.96 2363.11,1720.96 2363.39,1720.96 2363.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2363.39 1720.96 L2363.39 1720.96 L2363.68 1720.96 L2363.68 1720.96 L2363.39 1720.96 L2363.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2363.39,1720.96 2363.39,1720.96 2363.68,1720.96 2363.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2363.68 1720.96 L2363.68 1720.96 L2363.96 1720.96 L2363.96 1720.96 L2363.68 1720.96 L2363.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2363.68,1720.96 2363.68,1720.96 2363.96,1720.96 2363.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2363.96 1720.96 L2363.96 1720.96 L2364.24 1720.96 L2364.24 1720.96 L2363.96 1720.96 L2363.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2363.96,1720.96 2363.96,1720.96 2364.24,1720.96 2363.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2364.24 1720.96 L2364.24 1720.96 L2364.52 1720.96 L2364.52 1720.96 L2364.24 1720.96 L2364.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2364.24,1720.96 2364.24,1720.96 2364.52,1720.96 2364.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2364.52 1720.96 L2364.52 1720.96 L2364.8 1720.96 L2364.8 1720.96 L2364.52 1720.96 L2364.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2364.52,1720.96 2364.52,1720.96 2364.8,1720.96 2364.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2364.8 1720.96 L2364.8 1720.96 L2365.08 1720.96 L2365.08 1720.96 L2364.8 1720.96 L2364.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2364.8,1720.96 2364.8,1720.96 2365.08,1720.96 2364.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2365.08 1720.96 L2365.08 1720.96 L2365.37 1720.96 L2365.37 1720.96 L2365.08 1720.96 L2365.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2365.08,1720.96 2365.08,1720.96 2365.37,1720.96 2365.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2365.37 1720.96 L2365.37 1720.96 L2365.65 1720.96 L2365.65 1720.96 L2365.37 1720.96 L2365.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2365.37,1720.96 2365.37,1720.96 2365.65,1720.96 2365.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2365.65 1720.96 L2365.65 1720.96 L2365.93 1720.96 L2365.93 1720.96 L2365.65 1720.96 L2365.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2365.65,1720.96 2365.65,1720.96 2365.93,1720.96 2365.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2365.93 1720.96 L2365.93 1720.96 L2366.21 1720.96 L2366.21 1720.96 L2365.93 1720.96 L2365.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2365.93,1720.96 2365.93,1720.96 2366.21,1720.96 2365.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2366.21 1720.96 L2366.21 1720.96 L2366.49 1720.96 L2366.49 1720.96 L2366.21 1720.96 L2366.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2366.21,1720.96 2366.21,1720.96 2366.49,1720.96 2366.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2366.49 1720.96 L2366.49 1720.96 L2366.77 1720.96 L2366.77 1720.96 L2366.49 1720.96 L2366.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2366.49,1720.96 2366.49,1720.96 2366.77,1720.96 2366.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2366.77 1720.96 L2366.77 1720.96 L2367.06 1720.96 L2367.06 1720.96 L2366.77 1720.96 L2366.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2366.77,1720.96 2366.77,1720.96 2367.06,1720.96 2366.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2367.06 1720.96 L2367.06 1720.96 L2367.34 1720.96 L2367.34 1720.96 L2367.06 1720.96 L2367.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2367.06,1720.96 2367.06,1720.96 2367.34,1720.96 2367.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2367.34 1720.96 L2367.34 1720.96 L2367.62 1720.96 L2367.62 1720.96 L2367.34 1720.96 L2367.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2367.34,1720.96 2367.34,1720.96 2367.62,1720.96 2367.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2367.62 1720.96 L2367.62 1720.96 L2367.9 1720.96 L2367.9 1720.96 L2367.62 1720.96 L2367.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2367.62,1720.96 2367.62,1720.96 2367.9,1720.96 2367.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2367.9 1720.96 L2367.9 1720.96 L2368.18 1720.96 L2368.18 1720.96 L2367.9 1720.96 L2367.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2367.9,1720.96 2367.9,1720.96 2368.18,1720.96 2367.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2368.18 1720.96 L2368.18 1720.96 L2368.46 1720.96 L2368.46 1720.96 L2368.18 1720.96 L2368.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2368.18,1720.96 2368.18,1720.96 2368.46,1720.96 2368.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2368.46 1720.96 L2368.46 1720.96 L2368.75 1720.96 L2368.75 1720.96 L2368.46 1720.96 L2368.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2368.46,1720.96 2368.46,1720.96 2368.75,1720.96 2368.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2368.75 1720.96 L2368.75 1720.96 L2369.03 1720.96 L2369.03 1720.96 L2368.75 1720.96 L2368.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2368.75,1720.96 2368.75,1720.96 2369.03,1720.96 2368.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2369.03 1720.96 L2369.03 1720.96 L2369.31 1720.96 L2369.31 1720.96 L2369.03 1720.96 L2369.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2369.03,1720.96 2369.03,1720.96 2369.31,1720.96 2369.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2369.31 1720.96 L2369.31 1720.96 L2369.59 1720.96 L2369.59 1720.96 L2369.31 1720.96 L2369.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2369.31,1720.96 2369.31,1720.96 2369.59,1720.96 2369.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2369.59 1720.96 L2369.59 1720.96 L2369.87 1720.96 L2369.87 1720.96 L2369.59 1720.96 L2369.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2369.59,1720.96 2369.59,1720.96 2369.87,1720.96 2369.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2369.87 1720.96 L2369.87 1720.96 L2370.16 1720.96 L2370.16 1720.96 L2369.87 1720.96 L2369.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2369.87,1720.96 2369.87,1720.96 2370.16,1720.96 2369.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2370.16 1720.96 L2370.16 1720.96 L2370.44 1720.96 L2370.44 1720.96 L2370.16 1720.96 L2370.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2370.16,1720.96 2370.16,1720.96 2370.44,1720.96 2370.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2370.44 1720.96 L2370.44 1720.96 L2370.72 1720.96 L2370.72 1720.96 L2370.44 1720.96 L2370.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2370.44,1720.96 2370.44,1720.96 2370.72,1720.96 2370.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2370.72 1720.96 L2370.72 1720.96 L2371 1720.96 L2371 1720.96 L2370.72 1720.96 L2370.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2370.72,1720.96 2370.72,1720.96 2371,1720.96 2370.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2371 1720.96 L2371 1720.96 L2371.28 1720.96 L2371.28 1720.96 L2371 1720.96 L2371 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2371,1720.96 2371,1720.96 2371.28,1720.96 2371,1720.96 "/>
<path clip-path="url(#clip322)" d="M2371.28 1720.96 L2371.28 1720.96 L2371.56 1720.96 L2371.56 1720.96 L2371.28 1720.96 L2371.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2371.28,1720.96 2371.28,1720.96 2371.56,1720.96 2371.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2371.56 1720.96 L2371.56 1720.96 L2371.85 1720.96 L2371.85 1720.96 L2371.56 1720.96 L2371.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2371.56,1720.96 2371.56,1720.96 2371.85,1720.96 2371.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2371.85 1720.96 L2371.85 1720.96 L2372.13 1720.96 L2372.13 1720.96 L2371.85 1720.96 L2371.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2371.85,1720.96 2371.85,1720.96 2372.13,1720.96 2371.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2372.13 1720.96 L2372.13 1720.96 L2372.41 1720.96 L2372.41 1720.96 L2372.13 1720.96 L2372.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2372.13,1720.96 2372.13,1720.96 2372.41,1720.96 2372.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2372.41 1720.96 L2372.41 1720.96 L2372.69 1720.96 L2372.69 1720.96 L2372.41 1720.96 L2372.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2372.41,1720.96 2372.41,1720.96 2372.69,1720.96 2372.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2372.69 1720.96 L2372.69 1720.96 L2372.97 1720.96 L2372.97 1720.96 L2372.69 1720.96 L2372.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2372.69,1720.96 2372.69,1720.96 2372.97,1720.96 2372.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2372.97 1720.96 L2372.97 1720.96 L2373.25 1720.96 L2373.25 1720.96 L2372.97 1720.96 L2372.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2372.97,1720.96 2372.97,1720.96 2373.25,1720.96 2372.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2373.25 1720.96 L2373.25 1720.96 L2373.54 1720.96 L2373.54 1720.96 L2373.25 1720.96 L2373.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2373.25,1720.96 2373.25,1720.96 2373.54,1720.96 2373.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2373.54 1720.96 L2373.54 1720.96 L2373.82 1720.96 L2373.82 1720.96 L2373.54 1720.96 L2373.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2373.54,1720.96 2373.54,1720.96 2373.82,1720.96 2373.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2373.82 1720.96 L2373.82 1720.96 L2374.1 1720.96 L2374.1 1720.96 L2373.82 1720.96 L2373.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2373.82,1720.96 2373.82,1720.96 2374.1,1720.96 2373.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2374.1 1720.96 L2374.1 1720.96 L2374.38 1720.96 L2374.38 1720.96 L2374.1 1720.96 L2374.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2374.1,1720.96 2374.1,1720.96 2374.38,1720.96 2374.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2374.38 1720.96 L2374.38 1720.96 L2374.66 1720.96 L2374.66 1720.96 L2374.38 1720.96 L2374.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2374.38,1720.96 2374.38,1720.96 2374.66,1720.96 2374.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2374.66 1720.96 L2374.66 1720.96 L2374.94 1720.96 L2374.94 1720.96 L2374.66 1720.96 L2374.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2374.66,1720.96 2374.66,1720.96 2374.94,1720.96 2374.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2374.94 1720.96 L2374.94 1720.96 L2375.23 1720.96 L2375.23 1720.96 L2374.94 1720.96 L2374.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2374.94,1720.96 2374.94,1720.96 2375.23,1720.96 2374.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2375.23 1720.96 L2375.23 1720.96 L2375.51 1720.96 L2375.51 1720.96 L2375.23 1720.96 L2375.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2375.23,1720.96 2375.23,1720.96 2375.51,1720.96 2375.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2375.51 1720.96 L2375.51 1720.96 L2375.79 1720.96 L2375.79 1720.96 L2375.51 1720.96 L2375.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2375.51,1720.96 2375.51,1720.96 2375.79,1720.96 2375.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2375.79 1720.96 L2375.79 1720.96 L2376.07 1720.96 L2376.07 1720.96 L2375.79 1720.96 L2375.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2375.79,1720.96 2375.79,1720.96 2376.07,1720.96 2375.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2376.07 1720.96 L2376.07 1720.96 L2376.35 1720.96 L2376.35 1720.96 L2376.07 1720.96 L2376.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2376.07,1720.96 2376.07,1720.96 2376.35,1720.96 2376.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2376.35 1720.96 L2376.35 1720.96 L2376.63 1720.96 L2376.63 1720.96 L2376.35 1720.96 L2376.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2376.35,1720.96 2376.35,1720.96 2376.63,1720.96 2376.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2376.63 1720.96 L2376.63 1720.96 L2376.92 1720.96 L2376.92 1720.96 L2376.63 1720.96 L2376.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2376.63,1720.96 2376.63,1720.96 2376.92,1720.96 2376.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2376.92 1720.96 L2376.92 1720.96 L2377.2 1720.96 L2377.2 1720.96 L2376.92 1720.96 L2376.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2376.92,1720.96 2376.92,1720.96 2377.2,1720.96 2376.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2377.2 1720.96 L2377.2 1720.96 L2377.48 1720.96 L2377.48 1720.96 L2377.2 1720.96 L2377.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2377.2,1720.96 2377.2,1720.96 2377.48,1720.96 2377.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2377.48 1720.96 L2377.48 1720.96 L2377.76 1720.96 L2377.76 1720.96 L2377.48 1720.96 L2377.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2377.48,1720.96 2377.48,1720.96 2377.76,1720.96 2377.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2377.76 1720.96 L2377.76 1720.96 L2378.04 1720.96 L2378.04 1720.96 L2377.76 1720.96 L2377.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2377.76,1720.96 2377.76,1720.96 2378.04,1720.96 2377.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2378.04 1720.96 L2378.04 1720.96 L2378.33 1720.96 L2378.33 1720.96 L2378.04 1720.96 L2378.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2378.04,1720.96 2378.04,1720.96 2378.33,1720.96 2378.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2378.33 1720.96 L2378.33 1720.96 L2378.61 1720.96 L2378.61 1720.96 L2378.33 1720.96 L2378.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2378.33,1720.96 2378.33,1720.96 2378.61,1720.96 2378.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2378.61 1720.96 L2378.61 1720.96 L2378.89 1720.96 L2378.89 1720.96 L2378.61 1720.96 L2378.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2378.61,1720.96 2378.61,1720.96 2378.89,1720.96 2378.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2378.89 1720.96 L2378.89 1720.96 L2379.17 1720.96 L2379.17 1720.96 L2378.89 1720.96 L2378.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2378.89,1720.96 2378.89,1720.96 2379.17,1720.96 2378.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2379.17 1720.96 L2379.17 1720.96 L2379.45 1720.96 L2379.45 1720.96 L2379.17 1720.96 L2379.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2379.17,1720.96 2379.17,1720.96 2379.45,1720.96 2379.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2379.45 1720.96 L2379.45 1720.96 L2379.73 1720.96 L2379.73 1720.96 L2379.45 1720.96 L2379.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2379.45,1720.96 2379.45,1720.96 2379.73,1720.96 2379.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2379.73 1720.96 L2379.73 1720.96 L2380.02 1720.96 L2380.02 1720.96 L2379.73 1720.96 L2379.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2379.73,1720.96 2379.73,1720.96 2380.02,1720.96 2379.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2380.02 1720.96 L2380.02 1720.96 L2380.3 1720.96 L2380.3 1720.96 L2380.02 1720.96 L2380.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2380.02,1720.96 2380.02,1720.96 2380.3,1720.96 2380.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2380.3 1720.96 L2380.3 1720.96 L2380.58 1720.96 L2380.58 1720.96 L2380.3 1720.96 L2380.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2380.3,1720.96 2380.3,1720.96 2380.58,1720.96 2380.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2380.58 1720.96 L2380.58 1720.96 L2380.86 1720.96 L2380.86 1720.96 L2380.58 1720.96 L2380.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2380.58,1720.96 2380.58,1720.96 2380.86,1720.96 2380.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2380.86 1720.96 L2380.86 1720.96 L2381.14 1720.96 L2381.14 1720.96 L2380.86 1720.96 L2380.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2380.86,1720.96 2380.86,1720.96 2381.14,1720.96 2380.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2381.14 1720.96 L2381.14 1720.96 L2381.42 1720.96 L2381.42 1720.96 L2381.14 1720.96 L2381.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2381.14,1720.96 2381.14,1720.96 2381.42,1720.96 2381.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2381.42 1720.96 L2381.42 1720.96 L2381.71 1720.96 L2381.71 1720.96 L2381.42 1720.96 L2381.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2381.42,1720.96 2381.42,1720.96 2381.71,1720.96 2381.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2381.71 1720.96 L2381.71 1720.96 L2381.99 1720.96 L2381.99 1720.96 L2381.71 1720.96 L2381.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2381.71,1720.96 2381.71,1720.96 2381.99,1720.96 2381.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2381.99 1720.96 L2381.99 1720.96 L2382.27 1720.96 L2382.27 1720.96 L2381.99 1720.96 L2381.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2381.99,1720.96 2381.99,1720.96 2382.27,1720.96 2381.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2382.27 1720.96 L2382.27 1720.96 L2382.55 1720.96 L2382.55 1720.96 L2382.27 1720.96 L2382.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2382.27,1720.96 2382.27,1720.96 2382.55,1720.96 2382.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2382.55 1720.96 L2382.55 1720.96 L2382.83 1720.96 L2382.83 1720.96 L2382.55 1720.96 L2382.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2382.55,1720.96 2382.55,1720.96 2382.83,1720.96 2382.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2382.83 1720.96 L2382.83 1720.96 L2383.11 1720.96 L2383.11 1720.96 L2382.83 1720.96 L2382.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2382.83,1720.96 2382.83,1720.96 2383.11,1720.96 2382.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2383.11 1720.96 L2383.11 1720.96 L2383.4 1720.96 L2383.4 1720.96 L2383.11 1720.96 L2383.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2383.11,1720.96 2383.11,1720.96 2383.4,1720.96 2383.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2383.4 1720.96 L2383.4 1720.96 L2383.68 1720.96 L2383.68 1720.96 L2383.4 1720.96 L2383.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2383.4,1720.96 2383.4,1720.96 2383.68,1720.96 2383.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2383.68 1720.96 L2383.68 1720.96 L2383.96 1720.96 L2383.96 1720.96 L2383.68 1720.96 L2383.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2383.68,1720.96 2383.68,1720.96 2383.96,1720.96 2383.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2383.96 1720.96 L2383.96 1720.96 L2384.24 1720.96 L2384.24 1720.96 L2383.96 1720.96 L2383.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2383.96,1720.96 2383.96,1720.96 2384.24,1720.96 2383.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2384.24 1720.96 L2384.24 1720.96 L2384.52 1720.96 L2384.52 1720.96 L2384.24 1720.96 L2384.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2384.24,1720.96 2384.24,1720.96 2384.52,1720.96 2384.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2384.52 1720.96 L2384.52 1720.96 L2384.81 1720.96 L2384.81 1720.96 L2384.52 1720.96 L2384.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2384.52,1720.96 2384.52,1720.96 2384.81,1720.96 2384.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2384.81 1720.96 L2384.81 1720.96 L2385.09 1720.96 L2385.09 1720.96 L2384.81 1720.96 L2384.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2384.81,1720.96 2384.81,1720.96 2385.09,1720.96 2384.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2385.09 1720.96 L2385.09 1720.96 L2385.37 1720.96 L2385.37 1720.96 L2385.09 1720.96 L2385.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2385.09,1720.96 2385.09,1720.96 2385.37,1720.96 2385.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2385.37 1720.96 L2385.37 1720.96 L2385.65 1720.96 L2385.65 1720.96 L2385.37 1720.96 L2385.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2385.37,1720.96 2385.37,1720.96 2385.65,1720.96 2385.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2385.65 1720.96 L2385.65 1720.96 L2385.93 1720.96 L2385.93 1720.96 L2385.65 1720.96 L2385.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2385.65,1720.96 2385.65,1720.96 2385.93,1720.96 2385.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2385.93 1720.96 L2385.93 1720.96 L2386.21 1720.96 L2386.21 1720.96 L2385.93 1720.96 L2385.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2385.93,1720.96 2385.93,1720.96 2386.21,1720.96 2385.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2386.21 1720.96 L2386.21 1720.96 L2386.5 1720.96 L2386.5 1720.96 L2386.21 1720.96 L2386.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2386.21,1720.96 2386.21,1720.96 2386.5,1720.96 2386.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2386.5 1720.96 L2386.5 1720.96 L2386.78 1720.96 L2386.78 1720.96 L2386.5 1720.96 L2386.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2386.5,1720.96 2386.5,1720.96 2386.78,1720.96 2386.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2386.78 1720.96 L2386.78 1720.96 L2387.06 1720.96 L2387.06 1720.96 L2386.78 1720.96 L2386.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2386.78,1720.96 2386.78,1720.96 2387.06,1720.96 2386.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2387.06 1720.96 L2387.06 1720.96 L2387.34 1720.96 L2387.34 1720.96 L2387.06 1720.96 L2387.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2387.06,1720.96 2387.06,1720.96 2387.34,1720.96 2387.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2387.34 1720.96 L2387.34 1720.96 L2387.62 1720.96 L2387.62 1720.96 L2387.34 1720.96 L2387.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2387.34,1720.96 2387.34,1720.96 2387.62,1720.96 2387.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2387.62 1720.96 L2387.62 1720.96 L2387.9 1720.96 L2387.9 1720.96 L2387.62 1720.96 L2387.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2387.62,1720.96 2387.62,1720.96 2387.9,1720.96 2387.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2387.9 1720.96 L2387.9 1720.96 L2388.19 1720.96 L2388.19 1720.96 L2387.9 1720.96 L2387.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2387.9,1720.96 2387.9,1720.96 2388.19,1720.96 2387.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2388.19 1720.96 L2388.19 1720.96 L2388.47 1720.96 L2388.47 1720.96 L2388.19 1720.96 L2388.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2388.19,1720.96 2388.19,1720.96 2388.47,1720.96 2388.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2388.47 1720.96 L2388.47 1720.96 L2388.75 1720.96 L2388.75 1720.96 L2388.47 1720.96 L2388.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2388.47,1720.96 2388.47,1720.96 2388.75,1720.96 2388.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2388.75 1720.96 L2388.75 1720.96 L2389.03 1720.96 L2389.03 1720.96 L2388.75 1720.96 L2388.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2388.75,1720.96 2388.75,1720.96 2389.03,1720.96 2388.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2389.03 1720.96 L2389.03 1720.96 L2389.31 1720.96 L2389.31 1720.96 L2389.03 1720.96 L2389.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2389.03,1720.96 2389.03,1720.96 2389.31,1720.96 2389.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2389.31 1720.96 L2389.31 1720.96 L2389.59 1720.96 L2389.59 1720.96 L2389.31 1720.96 L2389.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2389.31,1720.96 2389.31,1720.96 2389.59,1720.96 2389.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2389.59 1720.96 L2389.59 1720.96 L2389.88 1720.96 L2389.88 1720.96 L2389.59 1720.96 L2389.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2389.59,1720.96 2389.59,1720.96 2389.88,1720.96 2389.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2389.88 1720.96 L2389.88 1720.96 L2390.16 1720.96 L2390.16 1720.96 L2389.88 1720.96 L2389.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2389.88,1720.96 2389.88,1720.96 2390.16,1720.96 2389.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2390.16 1720.96 L2390.16 1720.96 L2390.44 1720.96 L2390.44 1720.96 L2390.16 1720.96 L2390.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2390.16,1720.96 2390.16,1720.96 2390.44,1720.96 2390.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2390.44 1720.96 L2390.44 1720.96 L2390.72 1720.96 L2390.72 1720.96 L2390.44 1720.96 L2390.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2390.44,1720.96 2390.44,1720.96 2390.72,1720.96 2390.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2390.72 1720.96 L2390.72 1720.96 L2391 1720.96 L2391 1720.96 L2390.72 1720.96 L2390.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2390.72,1720.96 2390.72,1720.96 2391,1720.96 2390.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2391 1720.96 L2391 1720.96 L2391.28 1720.96 L2391.28 1720.96 L2391 1720.96 L2391 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2391,1720.96 2391,1720.96 2391.28,1720.96 2391,1720.96 "/>
<path clip-path="url(#clip322)" d="M2391.28 1720.96 L2391.28 1720.96 L2391.57 1720.96 L2391.57 1720.96 L2391.28 1720.96 L2391.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2391.28,1720.96 2391.28,1720.96 2391.57,1720.96 2391.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2391.57 1720.96 L2391.57 1720.96 L2391.85 1720.96 L2391.85 1720.96 L2391.57 1720.96 L2391.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2391.57,1720.96 2391.57,1720.96 2391.85,1720.96 2391.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2391.85 1720.96 L2391.85 1720.96 L2392.13 1720.96 L2392.13 1720.96 L2391.85 1720.96 L2391.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2391.85,1720.96 2391.85,1720.96 2392.13,1720.96 2391.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2392.13 1720.96 L2392.13 1720.96 L2392.41 1720.96 L2392.41 1720.96 L2392.13 1720.96 L2392.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2392.13,1720.96 2392.13,1720.96 2392.41,1720.96 2392.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2392.41 1720.96 L2392.41 1720.96 L2392.69 1720.96 L2392.69 1720.96 L2392.41 1720.96 L2392.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2392.41,1720.96 2392.41,1720.96 2392.69,1720.96 2392.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2392.69 1720.96 L2392.69 1720.96 L2392.98 1720.96 L2392.98 1720.96 L2392.69 1720.96 L2392.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2392.69,1720.96 2392.69,1720.96 2392.98,1720.96 2392.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2392.98 1720.96 L2392.98 1720.96 L2393.26 1720.96 L2393.26 1720.96 L2392.98 1720.96 L2392.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2392.98,1720.96 2392.98,1720.96 2393.26,1720.96 2392.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2393.26 1720.96 L2393.26 1720.96 L2393.54 1720.96 L2393.54 1720.96 L2393.26 1720.96 L2393.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2393.26,1720.96 2393.26,1720.96 2393.54,1720.96 2393.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2393.54 1720.96 L2393.54 1720.96 L2393.82 1720.96 L2393.82 1720.96 L2393.54 1720.96 L2393.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2393.54,1720.96 2393.54,1720.96 2393.82,1720.96 2393.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2393.82 1720.96 L2393.82 1720.96 L2394.1 1720.96 L2394.1 1720.96 L2393.82 1720.96 L2393.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2393.82,1720.96 2393.82,1720.96 2394.1,1720.96 2393.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2394.1 1720.96 L2394.1 1720.96 L2394.38 1720.96 L2394.38 1720.96 L2394.1 1720.96 L2394.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2394.1,1720.96 2394.1,1720.96 2394.38,1720.96 2394.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2394.38 1720.96 L2394.38 1720.96 L2394.67 1720.96 L2394.67 1720.96 L2394.38 1720.96 L2394.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2394.38,1720.96 2394.38,1720.96 2394.67,1720.96 2394.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2394.67 1720.96 L2394.67 1720.96 L2394.95 1720.96 L2394.95 1720.96 L2394.67 1720.96 L2394.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2394.67,1720.96 2394.67,1720.96 2394.95,1720.96 2394.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2394.95 1720.96 L2394.95 1720.96 L2395.23 1720.96 L2395.23 1720.96 L2394.95 1720.96 L2394.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2394.95,1720.96 2394.95,1720.96 2395.23,1720.96 2394.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2395.23 1720.96 L2395.23 1720.96 L2395.51 1720.96 L2395.51 1720.96 L2395.23 1720.96 L2395.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2395.23,1720.96 2395.23,1720.96 2395.51,1720.96 2395.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2395.51 1720.96 L2395.51 1720.96 L2395.79 1720.96 L2395.79 1720.96 L2395.51 1720.96 L2395.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2395.51,1720.96 2395.51,1720.96 2395.79,1720.96 2395.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2395.79 1720.96 L2395.79 1720.96 L2396.07 1720.96 L2396.07 1720.96 L2395.79 1720.96 L2395.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2395.79,1720.96 2395.79,1720.96 2396.07,1720.96 2395.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2396.07 1720.96 L2396.07 1720.96 L2396.36 1720.96 L2396.36 1720.96 L2396.07 1720.96 L2396.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2396.07,1720.96 2396.07,1720.96 2396.36,1720.96 2396.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2396.36 1720.96 L2396.36 1720.96 L2396.64 1720.96 L2396.64 1720.96 L2396.36 1720.96 L2396.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2396.36,1720.96 2396.36,1720.96 2396.64,1720.96 2396.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2396.64 1720.96 L2396.64 1720.96 L2396.92 1720.96 L2396.92 1720.96 L2396.64 1720.96 L2396.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2396.64,1720.96 2396.64,1720.96 2396.92,1720.96 2396.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2396.92 1720.96 L2396.92 1720.96 L2397.2 1720.96 L2397.2 1720.96 L2396.92 1720.96 L2396.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2396.92,1720.96 2396.92,1720.96 2397.2,1720.96 2396.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2397.2 1720.96 L2397.2 1720.96 L2397.48 1720.96 L2397.48 1720.96 L2397.2 1720.96 L2397.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2397.2,1720.96 2397.2,1720.96 2397.48,1720.96 2397.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2397.48 1720.96 L2397.48 1720.96 L2397.76 1720.96 L2397.76 1720.96 L2397.48 1720.96 L2397.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2397.48,1720.96 2397.48,1720.96 2397.76,1720.96 2397.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2397.76 1720.96 L2397.76 1720.96 L2398.05 1720.96 L2398.05 1720.96 L2397.76 1720.96 L2397.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2397.76,1720.96 2397.76,1720.96 2398.05,1720.96 2397.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2398.05 1720.96 L2398.05 1720.96 L2398.33 1720.96 L2398.33 1720.96 L2398.05 1720.96 L2398.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2398.05,1720.96 2398.05,1720.96 2398.33,1720.96 2398.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2398.33 1720.96 L2398.33 1720.96 L2398.61 1720.96 L2398.61 1720.96 L2398.33 1720.96 L2398.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2398.33,1720.96 2398.33,1720.96 2398.61,1720.96 2398.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2398.61 1720.96 L2398.61 1720.96 L2398.89 1720.96 L2398.89 1720.96 L2398.61 1720.96 L2398.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2398.61,1720.96 2398.61,1720.96 2398.89,1720.96 2398.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2398.89 1720.96 L2398.89 1720.96 L2399.17 1720.96 L2399.17 1720.96 L2398.89 1720.96 L2398.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2398.89,1720.96 2398.89,1720.96 2399.17,1720.96 2398.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2399.17 1720.96 L2399.17 1720.96 L2399.45 1720.96 L2399.45 1720.96 L2399.17 1720.96 L2399.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2399.17,1720.96 2399.17,1720.96 2399.45,1720.96 2399.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2399.45 1720.96 L2399.45 1720.96 L2399.74 1720.96 L2399.74 1720.96 L2399.45 1720.96 L2399.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2399.45,1720.96 2399.45,1720.96 2399.74,1720.96 2399.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2399.74 1720.96 L2399.74 1720.96 L2400.02 1720.96 L2400.02 1720.96 L2399.74 1720.96 L2399.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2399.74,1720.96 2399.74,1720.96 2400.02,1720.96 2399.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2400.02 1720.96 L2400.02 1720.96 L2400.3 1720.96 L2400.3 1720.96 L2400.02 1720.96 L2400.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2400.02,1720.96 2400.02,1720.96 2400.3,1720.96 2400.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2400.3 1720.96 L2400.3 1720.96 L2400.58 1720.96 L2400.58 1720.96 L2400.3 1720.96 L2400.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2400.3,1720.96 2400.3,1720.96 2400.58,1720.96 2400.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2400.58 1720.96 L2400.58 1720.96 L2400.86 1720.96 L2400.86 1720.96 L2400.58 1720.96 L2400.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2400.58,1720.96 2400.58,1720.96 2400.86,1720.96 2400.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2400.86 1720.96 L2400.86 1720.96 L2401.15 1720.96 L2401.15 1720.96 L2400.86 1720.96 L2400.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2400.86,1720.96 2400.86,1720.96 2401.15,1720.96 2400.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2401.15 1720.96 L2401.15 1720.96 L2401.43 1720.96 L2401.43 1720.96 L2401.15 1720.96 L2401.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2401.15,1720.96 2401.15,1720.96 2401.43,1720.96 2401.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2401.43 1720.96 L2401.43 1720.96 L2401.71 1720.96 L2401.71 1720.96 L2401.43 1720.96 L2401.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2401.43,1720.96 2401.43,1720.96 2401.71,1720.96 2401.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2401.71 1720.96 L2401.71 1720.96 L2401.99 1720.96 L2401.99 1720.96 L2401.71 1720.96 L2401.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2401.71,1720.96 2401.71,1720.96 2401.99,1720.96 2401.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2401.99 1720.96 L2401.99 1720.96 L2402.27 1720.96 L2402.27 1720.96 L2401.99 1720.96 L2401.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2401.99,1720.96 2401.99,1720.96 2402.27,1720.96 2401.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2402.27 1720.96 L2402.27 1720.96 L2402.55 1720.96 L2402.55 1720.96 L2402.27 1720.96 L2402.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2402.27,1720.96 2402.27,1720.96 2402.55,1720.96 2402.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2402.55 1720.96 L2402.55 1720.96 L2402.84 1720.96 L2402.84 1720.96 L2402.55 1720.96 L2402.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2402.55,1720.96 2402.55,1720.96 2402.84,1720.96 2402.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2402.84 1720.96 L2402.84 1720.96 L2403.12 1720.96 L2403.12 1720.96 L2402.84 1720.96 L2402.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2402.84,1720.96 2402.84,1720.96 2403.12,1720.96 2402.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2403.12 1720.96 L2403.12 1720.96 L2403.4 1720.96 L2403.4 1720.96 L2403.12 1720.96 L2403.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2403.12,1720.96 2403.12,1720.96 2403.4,1720.96 2403.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2403.4 1720.96 L2403.4 1720.96 L2403.68 1720.96 L2403.68 1720.96 L2403.4 1720.96 L2403.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2403.4,1720.96 2403.4,1720.96 2403.68,1720.96 2403.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2403.68 1720.96 L2403.68 1720.96 L2403.96 1720.96 L2403.96 1720.96 L2403.68 1720.96 L2403.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2403.68,1720.96 2403.68,1720.96 2403.96,1720.96 2403.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2403.96 1720.96 L2403.96 1720.96 L2404.24 1720.96 L2404.24 1720.96 L2403.96 1720.96 L2403.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2403.96,1720.96 2403.96,1720.96 2404.24,1720.96 2403.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2404.24 1720.96 L2404.24 1720.96 L2404.53 1720.96 L2404.53 1720.96 L2404.24 1720.96 L2404.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2404.24,1720.96 2404.24,1720.96 2404.53,1720.96 2404.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2404.53 1720.96 L2404.53 1720.96 L2404.81 1720.96 L2404.81 1720.96 L2404.53 1720.96 L2404.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2404.53,1720.96 2404.53,1720.96 2404.81,1720.96 2404.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2404.81 1720.96 L2404.81 1720.96 L2405.09 1720.96 L2405.09 1720.96 L2404.81 1720.96 L2404.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2404.81,1720.96 2404.81,1720.96 2405.09,1720.96 2404.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2405.09 1720.96 L2405.09 1720.96 L2405.37 1720.96 L2405.37 1720.96 L2405.09 1720.96 L2405.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2405.09,1720.96 2405.09,1720.96 2405.37,1720.96 2405.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2405.37 1720.96 L2405.37 1720.96 L2405.65 1720.96 L2405.65 1720.96 L2405.37 1720.96 L2405.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2405.37,1720.96 2405.37,1720.96 2405.65,1720.96 2405.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2405.65 1720.96 L2405.65 1720.96 L2405.93 1720.96 L2405.93 1720.96 L2405.65 1720.96 L2405.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2405.65,1720.96 2405.65,1720.96 2405.93,1720.96 2405.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2405.93 1720.96 L2405.93 1720.96 L2406.22 1720.96 L2406.22 1720.96 L2405.93 1720.96 L2405.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2405.93,1720.96 2405.93,1720.96 2406.22,1720.96 2405.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2406.22 1720.96 L2406.22 1720.96 L2406.5 1720.96 L2406.5 1720.96 L2406.22 1720.96 L2406.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2406.22,1720.96 2406.22,1720.96 2406.5,1720.96 2406.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2406.5 1720.96 L2406.5 1720.96 L2406.78 1720.96 L2406.78 1720.96 L2406.5 1720.96 L2406.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2406.5,1720.96 2406.5,1720.96 2406.78,1720.96 2406.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2406.78 1720.96 L2406.78 1720.96 L2407.06 1720.96 L2407.06 1720.96 L2406.78 1720.96 L2406.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2406.78,1720.96 2406.78,1720.96 2407.06,1720.96 2406.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2407.06 1720.96 L2407.06 1720.96 L2407.34 1720.96 L2407.34 1720.96 L2407.06 1720.96 L2407.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2407.06,1720.96 2407.06,1720.96 2407.34,1720.96 2407.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2407.34 1720.96 L2407.34 1720.96 L2407.62 1720.96 L2407.62 1720.96 L2407.34 1720.96 L2407.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2407.34,1720.96 2407.34,1720.96 2407.62,1720.96 2407.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2407.62 1720.96 L2407.62 1720.96 L2407.91 1720.96 L2407.91 1720.96 L2407.62 1720.96 L2407.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2407.62,1720.96 2407.62,1720.96 2407.91,1720.96 2407.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2407.91 1720.96 L2407.91 1720.96 L2408.19 1720.96 L2408.19 1720.96 L2407.91 1720.96 L2407.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2407.91,1720.96 2407.91,1720.96 2408.19,1720.96 2407.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2408.19 1720.96 L2408.19 1720.96 L2408.47 1720.96 L2408.47 1720.96 L2408.19 1720.96 L2408.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2408.19,1720.96 2408.19,1720.96 2408.47,1720.96 2408.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2408.47 1720.96 L2408.47 1720.96 L2408.75 1720.96 L2408.75 1720.96 L2408.47 1720.96 L2408.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2408.47,1720.96 2408.47,1720.96 2408.75,1720.96 2408.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2408.75 1720.96 L2408.75 1720.96 L2409.03 1720.96 L2409.03 1720.96 L2408.75 1720.96 L2408.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2408.75,1720.96 2408.75,1720.96 2409.03,1720.96 2408.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2409.03 1720.96 L2409.03 1720.96 L2409.32 1720.96 L2409.32 1720.96 L2409.03 1720.96 L2409.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2409.03,1720.96 2409.03,1720.96 2409.32,1720.96 2409.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2409.32 1720.96 L2409.32 1720.96 L2409.6 1720.96 L2409.6 1720.96 L2409.32 1720.96 L2409.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2409.32,1720.96 2409.32,1720.96 2409.6,1720.96 2409.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2409.6 1720.96 L2409.6 1720.96 L2409.88 1720.96 L2409.88 1720.96 L2409.6 1720.96 L2409.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2409.6,1720.96 2409.6,1720.96 2409.88,1720.96 2409.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2409.88 1720.96 L2409.88 1720.96 L2410.16 1720.96 L2410.16 1720.96 L2409.88 1720.96 L2409.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2409.88,1720.96 2409.88,1720.96 2410.16,1720.96 2409.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2410.16 1720.96 L2410.16 1720.96 L2410.44 1720.96 L2410.44 1720.96 L2410.16 1720.96 L2410.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2410.16,1720.96 2410.16,1720.96 2410.44,1720.96 2410.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2410.44 1720.96 L2410.44 1720.96 L2410.72 1720.96 L2410.72 1720.96 L2410.44 1720.96 L2410.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2410.44,1720.96 2410.44,1720.96 2410.72,1720.96 2410.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2410.72 1720.96 L2410.72 1720.96 L2411.01 1720.96 L2411.01 1720.96 L2410.72 1720.96 L2410.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2410.72,1720.96 2410.72,1720.96 2411.01,1720.96 2410.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2411.01 1720.96 L2411.01 1720.96 L2411.29 1720.96 L2411.29 1720.96 L2411.01 1720.96 L2411.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2411.01,1720.96 2411.01,1720.96 2411.29,1720.96 2411.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2411.29 1720.96 L2411.29 1720.96 L2411.57 1720.96 L2411.57 1720.96 L2411.29 1720.96 L2411.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2411.29,1720.96 2411.29,1720.96 2411.57,1720.96 2411.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2411.57 1720.96 L2411.57 1720.96 L2411.85 1720.96 L2411.85 1720.96 L2411.57 1720.96 L2411.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2411.57,1720.96 2411.57,1720.96 2411.85,1720.96 2411.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2411.85 1720.96 L2411.85 1720.96 L2412.13 1720.96 L2412.13 1720.96 L2411.85 1720.96 L2411.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2411.85,1720.96 2411.85,1720.96 2412.13,1720.96 2411.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2412.13 1720.96 L2412.13 1720.96 L2412.41 1720.96 L2412.41 1720.96 L2412.13 1720.96 L2412.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2412.13,1720.96 2412.13,1720.96 2412.41,1720.96 2412.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2412.41 1720.96 L2412.41 1720.96 L2412.7 1720.96 L2412.7 1720.96 L2412.41 1720.96 L2412.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2412.41,1720.96 2412.41,1720.96 2412.7,1720.96 2412.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2412.7 1720.96 L2412.7 1720.96 L2412.98 1720.96 L2412.98 1720.96 L2412.7 1720.96 L2412.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2412.7,1720.96 2412.7,1720.96 2412.98,1720.96 2412.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2412.98 1720.96 L2412.98 1720.96 L2413.26 1720.96 L2413.26 1720.96 L2412.98 1720.96 L2412.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2412.98,1720.96 2412.98,1720.96 2413.26,1720.96 2412.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2413.26 1720.96 L2413.26 1720.96 L2413.54 1720.96 L2413.54 1720.96 L2413.26 1720.96 L2413.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2413.26,1720.96 2413.26,1720.96 2413.54,1720.96 2413.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2413.54 1720.96 L2413.54 1720.96 L2413.82 1720.96 L2413.82 1720.96 L2413.54 1720.96 L2413.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2413.54,1720.96 2413.54,1720.96 2413.82,1720.96 2413.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2413.82 1720.96 L2413.82 1720.96 L2414.1 1720.96 L2414.1 1720.96 L2413.82 1720.96 L2413.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2413.82,1720.96 2413.82,1720.96 2414.1,1720.96 2413.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2414.1 1720.96 L2414.1 1720.96 L2414.39 1720.96 L2414.39 1720.96 L2414.1 1720.96 L2414.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2414.1,1720.96 2414.1,1720.96 2414.39,1720.96 2414.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2414.39 1720.96 L2414.39 1720.96 L2414.67 1720.96 L2414.67 1720.96 L2414.39 1720.96 L2414.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2414.39,1720.96 2414.39,1720.96 2414.67,1720.96 2414.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2414.67 1720.96 L2414.67 1720.96 L2414.95 1720.96 L2414.95 1720.96 L2414.67 1720.96 L2414.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2414.67,1720.96 2414.67,1720.96 2414.95,1720.96 2414.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2414.95 1720.96 L2414.95 1720.96 L2415.23 1720.96 L2415.23 1720.96 L2414.95 1720.96 L2414.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2414.95,1720.96 2414.95,1720.96 2415.23,1720.96 2414.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2415.23 1720.96 L2415.23 1720.96 L2415.51 1720.96 L2415.51 1720.96 L2415.23 1720.96 L2415.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2415.23,1720.96 2415.23,1720.96 2415.51,1720.96 2415.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2415.51 1720.96 L2415.51 1720.96 L2415.79 1720.96 L2415.79 1720.96 L2415.51 1720.96 L2415.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2415.51,1720.96 2415.51,1720.96 2415.79,1720.96 2415.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2415.79 1720.96 L2415.79 1720.96 L2416.08 1720.96 L2416.08 1720.96 L2415.79 1720.96 L2415.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2415.79,1720.96 2415.79,1720.96 2416.08,1720.96 2415.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2416.08 1720.96 L2416.08 1720.96 L2416.36 1720.96 L2416.36 1720.96 L2416.08 1720.96 L2416.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2416.08,1720.96 2416.08,1720.96 2416.36,1720.96 2416.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2416.36 1720.96 L2416.36 1720.96 L2416.64 1720.96 L2416.64 1720.96 L2416.36 1720.96 L2416.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2416.36,1720.96 2416.36,1720.96 2416.64,1720.96 2416.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2416.64 1720.96 L2416.64 1720.96 L2416.92 1720.96 L2416.92 1720.96 L2416.64 1720.96 L2416.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2416.64,1720.96 2416.64,1720.96 2416.92,1720.96 2416.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2416.92 1720.96 L2416.92 1720.96 L2417.2 1720.96 L2417.2 1720.96 L2416.92 1720.96 L2416.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2416.92,1720.96 2416.92,1720.96 2417.2,1720.96 2416.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2417.2 1720.96 L2417.2 1720.96 L2417.49 1720.96 L2417.49 1720.96 L2417.2 1720.96 L2417.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2417.2,1720.96 2417.2,1720.96 2417.49,1720.96 2417.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2417.49 1720.96 L2417.49 1720.96 L2417.77 1720.96 L2417.77 1720.96 L2417.49 1720.96 L2417.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2417.49,1720.96 2417.49,1720.96 2417.77,1720.96 2417.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2417.77 1720.96 L2417.77 1720.96 L2418.05 1720.96 L2418.05 1720.96 L2417.77 1720.96 L2417.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2417.77,1720.96 2417.77,1720.96 2418.05,1720.96 2417.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2418.05 1720.96 L2418.05 1720.96 L2418.33 1720.96 L2418.33 1720.96 L2418.05 1720.96 L2418.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2418.05,1720.96 2418.05,1720.96 2418.33,1720.96 2418.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2418.33 1720.96 L2418.33 1720.96 L2418.61 1720.96 L2418.61 1720.96 L2418.33 1720.96 L2418.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2418.33,1720.96 2418.33,1720.96 2418.61,1720.96 2418.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2418.61 1720.96 L2418.61 1720.96 L2418.89 1720.96 L2418.89 1720.96 L2418.61 1720.96 L2418.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2418.61,1720.96 2418.61,1720.96 2418.89,1720.96 2418.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2418.89 1720.96 L2418.89 1720.96 L2419.18 1720.96 L2419.18 1720.96 L2418.89 1720.96 L2418.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2418.89,1720.96 2418.89,1720.96 2419.18,1720.96 2418.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2419.18 1720.96 L2419.18 1720.96 L2419.46 1720.96 L2419.46 1720.96 L2419.18 1720.96 L2419.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2419.18,1720.96 2419.18,1720.96 2419.46,1720.96 2419.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2419.46 1720.96 L2419.46 1720.96 L2419.74 1720.96 L2419.74 1720.96 L2419.46 1720.96 L2419.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2419.46,1720.96 2419.46,1720.96 2419.74,1720.96 2419.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2419.74 1720.96 L2419.74 1720.96 L2420.02 1720.96 L2420.02 1720.96 L2419.74 1720.96 L2419.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2419.74,1720.96 2419.74,1720.96 2420.02,1720.96 2419.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2420.02 1720.96 L2420.02 1720.96 L2420.3 1720.96 L2420.3 1720.96 L2420.02 1720.96 L2420.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2420.02,1720.96 2420.02,1720.96 2420.3,1720.96 2420.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2420.3 1720.96 L2420.3 1720.96 L2420.58 1720.96 L2420.58 1720.96 L2420.3 1720.96 L2420.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2420.3,1720.96 2420.3,1720.96 2420.58,1720.96 2420.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2420.58 1720.96 L2420.58 1720.96 L2420.87 1720.96 L2420.87 1720.96 L2420.58 1720.96 L2420.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2420.58,1720.96 2420.58,1720.96 2420.87,1720.96 2420.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2420.87 1720.96 L2420.87 1720.96 L2421.15 1720.96 L2421.15 1720.96 L2420.87 1720.96 L2420.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2420.87,1720.96 2420.87,1720.96 2421.15,1720.96 2420.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2421.15 1720.96 L2421.15 1720.96 L2421.43 1720.96 L2421.43 1720.96 L2421.15 1720.96 L2421.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2421.15,1720.96 2421.15,1720.96 2421.43,1720.96 2421.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2421.43 1720.96 L2421.43 1720.96 L2421.71 1720.96 L2421.71 1720.96 L2421.43 1720.96 L2421.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2421.43,1720.96 2421.43,1720.96 2421.71,1720.96 2421.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2421.71 1720.96 L2421.71 1720.96 L2421.99 1720.96 L2421.99 1720.96 L2421.71 1720.96 L2421.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2421.71,1720.96 2421.71,1720.96 2421.99,1720.96 2421.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2421.99 1720.96 L2421.99 1720.96 L2422.27 1720.96 L2422.27 1720.96 L2421.99 1720.96 L2421.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2421.99,1720.96 2421.99,1720.96 2422.27,1720.96 2421.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2422.27 1720.96 L2422.27 1720.96 L2422.56 1720.96 L2422.56 1720.96 L2422.27 1720.96 L2422.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2422.27,1720.96 2422.27,1720.96 2422.56,1720.96 2422.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2422.56 1720.96 L2422.56 1720.96 L2422.84 1720.96 L2422.84 1720.96 L2422.56 1720.96 L2422.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2422.56,1720.96 2422.56,1720.96 2422.84,1720.96 2422.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2422.84 1720.96 L2422.84 1720.96 L2423.12 1720.96 L2423.12 1720.96 L2422.84 1720.96 L2422.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2422.84,1720.96 2422.84,1720.96 2423.12,1720.96 2422.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2423.12 1720.96 L2423.12 1720.96 L2423.4 1720.96 L2423.4 1720.96 L2423.12 1720.96 L2423.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2423.12,1720.96 2423.12,1720.96 2423.4,1720.96 2423.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2423.4 1720.96 L2423.4 1720.96 L2423.68 1720.96 L2423.68 1720.96 L2423.4 1720.96 L2423.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2423.4,1720.96 2423.4,1720.96 2423.68,1720.96 2423.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2423.68 1720.96 L2423.68 1720.96 L2423.96 1720.96 L2423.96 1720.96 L2423.68 1720.96 L2423.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2423.68,1720.96 2423.68,1720.96 2423.96,1720.96 2423.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2423.96 1720.96 L2423.96 1720.96 L2424.25 1720.96 L2424.25 1720.96 L2423.96 1720.96 L2423.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2423.96,1720.96 2423.96,1720.96 2424.25,1720.96 2423.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2424.25 1720.96 L2424.25 1720.96 L2424.53 1720.96 L2424.53 1720.96 L2424.25 1720.96 L2424.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2424.25,1720.96 2424.25,1720.96 2424.53,1720.96 2424.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2424.53 1720.96 L2424.53 1720.96 L2424.81 1720.96 L2424.81 1720.96 L2424.53 1720.96 L2424.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2424.53,1720.96 2424.53,1720.96 2424.81,1720.96 2424.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2424.81 1720.96 L2424.81 1720.96 L2425.09 1720.96 L2425.09 1720.96 L2424.81 1720.96 L2424.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2424.81,1720.96 2424.81,1720.96 2425.09,1720.96 2424.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2425.09 1720.96 L2425.09 1720.96 L2425.37 1720.96 L2425.37 1720.96 L2425.09 1720.96 L2425.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2425.09,1720.96 2425.09,1720.96 2425.37,1720.96 2425.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2425.37 1720.96 L2425.37 1720.96 L2425.66 1720.96 L2425.66 1720.96 L2425.37 1720.96 L2425.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2425.37,1720.96 2425.37,1720.96 2425.66,1720.96 2425.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2425.66 1720.96 L2425.66 1720.96 L2425.94 1720.96 L2425.94 1720.96 L2425.66 1720.96 L2425.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2425.66,1720.96 2425.66,1720.96 2425.94,1720.96 2425.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2425.94 1720.96 L2425.94 1720.96 L2426.22 1720.96 L2426.22 1720.96 L2425.94 1720.96 L2425.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2425.94,1720.96 2425.94,1720.96 2426.22,1720.96 2425.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2426.22 1720.96 L2426.22 1720.96 L2426.5 1720.96 L2426.5 1720.96 L2426.22 1720.96 L2426.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2426.22,1720.96 2426.22,1720.96 2426.5,1720.96 2426.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2426.5 1720.96 L2426.5 1720.96 L2426.78 1720.96 L2426.78 1720.96 L2426.5 1720.96 L2426.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2426.5,1720.96 2426.5,1720.96 2426.78,1720.96 2426.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2426.78 1720.96 L2426.78 1720.96 L2427.06 1720.96 L2427.06 1720.96 L2426.78 1720.96 L2426.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2426.78,1720.96 2426.78,1720.96 2427.06,1720.96 2426.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2427.06 1720.96 L2427.06 1720.96 L2427.35 1720.96 L2427.35 1720.96 L2427.06 1720.96 L2427.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2427.06,1720.96 2427.06,1720.96 2427.35,1720.96 2427.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2427.35 1720.96 L2427.35 1720.96 L2427.63 1720.96 L2427.63 1720.96 L2427.35 1720.96 L2427.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2427.35,1720.96 2427.35,1720.96 2427.63,1720.96 2427.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2427.63 1720.96 L2427.63 1720.96 L2427.91 1720.96 L2427.91 1720.96 L2427.63 1720.96 L2427.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2427.63,1720.96 2427.63,1720.96 2427.91,1720.96 2427.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2427.91 1720.96 L2427.91 1720.96 L2428.19 1720.96 L2428.19 1720.96 L2427.91 1720.96 L2427.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2427.91,1720.96 2427.91,1720.96 2428.19,1720.96 2427.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2428.19 1720.96 L2428.19 1720.96 L2428.47 1720.96 L2428.47 1720.96 L2428.19 1720.96 L2428.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2428.19,1720.96 2428.19,1720.96 2428.47,1720.96 2428.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2428.47 1720.96 L2428.47 1720.96 L2428.75 1720.96 L2428.75 1720.96 L2428.47 1720.96 L2428.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2428.47,1720.96 2428.47,1720.96 2428.75,1720.96 2428.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2428.75 1720.96 L2428.75 1720.96 L2429.04 1720.96 L2429.04 1720.96 L2428.75 1720.96 L2428.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2428.75,1720.96 2428.75,1720.96 2429.04,1720.96 2428.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2429.04 1720.96 L2429.04 1720.96 L2429.32 1720.96 L2429.32 1720.96 L2429.04 1720.96 L2429.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2429.04,1720.96 2429.04,1720.96 2429.32,1720.96 2429.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2429.32 1720.96 L2429.32 1720.96 L2429.6 1720.96 L2429.6 1720.96 L2429.32 1720.96 L2429.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2429.32,1720.96 2429.32,1720.96 2429.6,1720.96 2429.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2429.6 1720.96 L2429.6 1720.96 L2429.88 1720.96 L2429.88 1720.96 L2429.6 1720.96 L2429.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2429.6,1720.96 2429.6,1720.96 2429.88,1720.96 2429.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2429.88 1720.96 L2429.88 1720.96 L2430.16 1720.96 L2430.16 1720.96 L2429.88 1720.96 L2429.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2429.88,1720.96 2429.88,1720.96 2430.16,1720.96 2429.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2430.16 1720.96 L2430.16 1720.96 L2430.44 1720.96 L2430.44 1720.96 L2430.16 1720.96 L2430.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2430.16,1720.96 2430.16,1720.96 2430.44,1720.96 2430.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2430.44 1720.96 L2430.44 1720.96 L2430.73 1720.96 L2430.73 1720.96 L2430.44 1720.96 L2430.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2430.44,1720.96 2430.44,1720.96 2430.73,1720.96 2430.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2430.73 1720.96 L2430.73 1720.96 L2431.01 1720.96 L2431.01 1720.96 L2430.73 1720.96 L2430.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2430.73,1720.96 2430.73,1720.96 2431.01,1720.96 2430.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2431.01 1720.96 L2431.01 1720.96 L2431.29 1720.96 L2431.29 1720.96 L2431.01 1720.96 L2431.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2431.01,1720.96 2431.01,1720.96 2431.29,1720.96 2431.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2431.29 1720.96 L2431.29 1720.96 L2431.57 1720.96 L2431.57 1720.96 L2431.29 1720.96 L2431.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2431.29,1720.96 2431.29,1720.96 2431.57,1720.96 2431.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2431.57 1720.96 L2431.57 1720.96 L2431.85 1720.96 L2431.85 1720.96 L2431.57 1720.96 L2431.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2431.57,1720.96 2431.57,1720.96 2431.85,1720.96 2431.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2431.85 1720.96 L2431.85 1720.96 L2432.13 1720.96 L2432.13 1720.96 L2431.85 1720.96 L2431.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2431.85,1720.96 2431.85,1720.96 2432.13,1720.96 2431.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2432.13 1720.96 L2432.13 1720.96 L2432.42 1720.96 L2432.42 1720.96 L2432.13 1720.96 L2432.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2432.13,1720.96 2432.13,1720.96 2432.42,1720.96 2432.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2432.42 1720.96 L2432.42 1720.96 L2432.7 1720.96 L2432.7 1720.96 L2432.42 1720.96 L2432.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2432.42,1720.96 2432.42,1720.96 2432.7,1720.96 2432.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2432.7 1720.96 L2432.7 1720.96 L2432.98 1720.96 L2432.98 1720.96 L2432.7 1720.96 L2432.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2432.7,1720.96 2432.7,1720.96 2432.98,1720.96 2432.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2432.98 1720.96 L2432.98 1720.96 L2433.26 1720.96 L2433.26 1720.96 L2432.98 1720.96 L2432.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2432.98,1720.96 2432.98,1720.96 2433.26,1720.96 2432.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2433.26 1720.96 L2433.26 1720.96 L2433.54 1720.96 L2433.54 1720.96 L2433.26 1720.96 L2433.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2433.26,1720.96 2433.26,1720.96 2433.54,1720.96 2433.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2433.54 1720.96 L2433.54 1720.96 L2433.83 1720.96 L2433.83 1720.96 L2433.54 1720.96 L2433.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2433.54,1720.96 2433.54,1720.96 2433.83,1720.96 2433.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2433.83 1720.96 L2433.83 1720.96 L2434.11 1720.96 L2434.11 1720.96 L2433.83 1720.96 L2433.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2433.83,1720.96 2433.83,1720.96 2434.11,1720.96 2433.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2434.11 1720.96 L2434.11 1720.96 L2434.39 1720.96 L2434.39 1720.96 L2434.11 1720.96 L2434.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2434.11,1720.96 2434.11,1720.96 2434.39,1720.96 2434.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2434.39 1720.96 L2434.39 1720.96 L2434.67 1720.96 L2434.67 1720.96 L2434.39 1720.96 L2434.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2434.39,1720.96 2434.39,1720.96 2434.67,1720.96 2434.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2434.67 1720.96 L2434.67 1720.96 L2434.95 1720.96 L2434.95 1720.96 L2434.67 1720.96 L2434.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2434.67,1720.96 2434.67,1720.96 2434.95,1720.96 2434.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2434.95 1720.96 L2434.95 1720.96 L2435.23 1720.96 L2435.23 1720.96 L2434.95 1720.96 L2434.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2434.95,1720.96 2434.95,1720.96 2435.23,1720.96 2434.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2435.23 1720.96 L2435.23 1720.96 L2435.52 1720.96 L2435.52 1720.96 L2435.23 1720.96 L2435.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2435.23,1720.96 2435.23,1720.96 2435.52,1720.96 2435.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2435.52 1720.96 L2435.52 1720.96 L2435.8 1720.96 L2435.8 1720.96 L2435.52 1720.96 L2435.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2435.52,1720.96 2435.52,1720.96 2435.8,1720.96 2435.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2435.8 1720.96 L2435.8 1720.96 L2436.08 1720.96 L2436.08 1720.96 L2435.8 1720.96 L2435.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2435.8,1720.96 2435.8,1720.96 2436.08,1720.96 2435.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2436.08 1720.96 L2436.08 1720.96 L2436.36 1720.96 L2436.36 1720.96 L2436.08 1720.96 L2436.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2436.08,1720.96 2436.08,1720.96 2436.36,1720.96 2436.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2436.36 1720.96 L2436.36 1720.96 L2436.64 1720.96 L2436.64 1720.96 L2436.36 1720.96 L2436.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2436.36,1720.96 2436.36,1720.96 2436.64,1720.96 2436.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2436.64 1720.96 L2436.64 1720.96 L2436.92 1720.96 L2436.92 1720.96 L2436.64 1720.96 L2436.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2436.64,1720.96 2436.64,1720.96 2436.92,1720.96 2436.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2436.92 1720.96 L2436.92 1720.96 L2437.21 1720.96 L2437.21 1720.96 L2436.92 1720.96 L2436.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2436.92,1720.96 2436.92,1720.96 2437.21,1720.96 2436.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2437.21 1720.96 L2437.21 1720.96 L2437.49 1720.96 L2437.49 1720.96 L2437.21 1720.96 L2437.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2437.21,1720.96 2437.21,1720.96 2437.49,1720.96 2437.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2437.49 1720.96 L2437.49 1720.96 L2437.77 1720.96 L2437.77 1720.96 L2437.49 1720.96 L2437.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2437.49,1720.96 2437.49,1720.96 2437.77,1720.96 2437.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2437.77 1720.96 L2437.77 1720.96 L2438.05 1720.96 L2438.05 1720.96 L2437.77 1720.96 L2437.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2437.77,1720.96 2437.77,1720.96 2438.05,1720.96 2437.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2438.05 1720.96 L2438.05 1720.96 L2438.33 1720.96 L2438.33 1720.96 L2438.05 1720.96 L2438.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2438.05,1720.96 2438.05,1720.96 2438.33,1720.96 2438.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2438.33 1720.96 L2438.33 1720.96 L2438.61 1720.96 L2438.61 1720.96 L2438.33 1720.96 L2438.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2438.33,1720.96 2438.33,1720.96 2438.61,1720.96 2438.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2438.61 1720.96 L2438.61 1720.96 L2438.9 1720.96 L2438.9 1720.96 L2438.61 1720.96 L2438.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2438.61,1720.96 2438.61,1720.96 2438.9,1720.96 2438.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2438.9 1720.96 L2438.9 1720.96 L2439.18 1720.96 L2439.18 1720.96 L2438.9 1720.96 L2438.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2438.9,1720.96 2438.9,1720.96 2439.18,1720.96 2438.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2439.18 1720.96 L2439.18 1720.96 L2439.46 1720.96 L2439.46 1720.96 L2439.18 1720.96 L2439.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2439.18,1720.96 2439.18,1720.96 2439.46,1720.96 2439.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2439.46 1720.96 L2439.46 1720.96 L2439.74 1720.96 L2439.74 1720.96 L2439.46 1720.96 L2439.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2439.46,1720.96 2439.46,1720.96 2439.74,1720.96 2439.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2439.74 1720.96 L2439.74 1720.96 L2440.02 1720.96 L2440.02 1720.96 L2439.74 1720.96 L2439.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2439.74,1720.96 2439.74,1720.96 2440.02,1720.96 2439.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2440.02 1720.96 L2440.02 1720.96 L2440.3 1720.96 L2440.3 1720.96 L2440.02 1720.96 L2440.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2440.02,1720.96 2440.02,1720.96 2440.3,1720.96 2440.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2440.3 1720.96 L2440.3 1720.96 L2440.59 1720.96 L2440.59 1720.96 L2440.3 1720.96 L2440.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2440.3,1720.96 2440.3,1720.96 2440.59,1720.96 2440.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2440.59 1720.96 L2440.59 1720.96 L2440.87 1720.96 L2440.87 1720.96 L2440.59 1720.96 L2440.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2440.59,1720.96 2440.59,1720.96 2440.87,1720.96 2440.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2440.87 1720.96 L2440.87 1720.96 L2441.15 1720.96 L2441.15 1720.96 L2440.87 1720.96 L2440.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2440.87,1720.96 2440.87,1720.96 2441.15,1720.96 2440.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2441.15 1720.96 L2441.15 1720.96 L2441.43 1720.96 L2441.43 1720.96 L2441.15 1720.96 L2441.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2441.15,1720.96 2441.15,1720.96 2441.43,1720.96 2441.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2441.43 1720.96 L2441.43 1720.96 L2441.71 1720.96 L2441.71 1720.96 L2441.43 1720.96 L2441.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2441.43,1720.96 2441.43,1720.96 2441.71,1720.96 2441.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2441.71 1720.96 L2441.71 1720.96 L2442 1720.96 L2442 1720.96 L2441.71 1720.96 L2441.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2441.71,1720.96 2441.71,1720.96 2442,1720.96 2441.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2442 1720.96 L2442 1720.96 L2442.28 1720.96 L2442.28 1720.96 L2442 1720.96 L2442 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2442,1720.96 2442,1720.96 2442.28,1720.96 2442,1720.96 "/>
<path clip-path="url(#clip322)" d="M2442.28 1720.96 L2442.28 1720.96 L2442.56 1720.96 L2442.56 1720.96 L2442.28 1720.96 L2442.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2442.28,1720.96 2442.28,1720.96 2442.56,1720.96 2442.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2442.56 1720.96 L2442.56 1720.96 L2442.84 1720.96 L2442.84 1720.96 L2442.56 1720.96 L2442.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2442.56,1720.96 2442.56,1720.96 2442.84,1720.96 2442.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2442.84 1720.96 L2442.84 1720.96 L2443.12 1720.96 L2443.12 1720.96 L2442.84 1720.96 L2442.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2442.84,1720.96 2442.84,1720.96 2443.12,1720.96 2442.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2443.12 1720.96 L2443.12 1720.96 L2443.4 1720.96 L2443.4 1720.96 L2443.12 1720.96 L2443.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2443.12,1720.96 2443.12,1720.96 2443.4,1720.96 2443.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2443.4 1720.96 L2443.4 1720.96 L2443.69 1720.96 L2443.69 1720.96 L2443.4 1720.96 L2443.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2443.4,1720.96 2443.4,1720.96 2443.69,1720.96 2443.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2443.69 1720.96 L2443.69 1720.96 L2443.97 1720.96 L2443.97 1720.96 L2443.69 1720.96 L2443.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2443.69,1720.96 2443.69,1720.96 2443.97,1720.96 2443.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2443.97 1720.96 L2443.97 1720.96 L2444.25 1720.96 L2444.25 1720.96 L2443.97 1720.96 L2443.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2443.97,1720.96 2443.97,1720.96 2444.25,1720.96 2443.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2444.25 1720.96 L2444.25 1720.96 L2444.53 1720.96 L2444.53 1720.96 L2444.25 1720.96 L2444.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2444.25,1720.96 2444.25,1720.96 2444.53,1720.96 2444.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2444.53 1720.96 L2444.53 1720.96 L2444.81 1720.96 L2444.81 1720.96 L2444.53 1720.96 L2444.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2444.53,1720.96 2444.53,1720.96 2444.81,1720.96 2444.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2444.81 1720.96 L2444.81 1720.96 L2445.09 1720.96 L2445.09 1720.96 L2444.81 1720.96 L2444.81 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2444.81,1720.96 2444.81,1720.96 2445.09,1720.96 2444.81,1720.96 "/>
<path clip-path="url(#clip322)" d="M2445.09 1720.96 L2445.09 1720.96 L2445.38 1720.96 L2445.38 1720.96 L2445.09 1720.96 L2445.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2445.09,1720.96 2445.09,1720.96 2445.38,1720.96 2445.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2445.38 1720.96 L2445.38 1720.96 L2445.66 1720.96 L2445.66 1720.96 L2445.38 1720.96 L2445.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2445.38,1720.96 2445.38,1720.96 2445.66,1720.96 2445.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2445.66 1720.96 L2445.66 1720.96 L2445.94 1720.96 L2445.94 1720.96 L2445.66 1720.96 L2445.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2445.66,1720.96 2445.66,1720.96 2445.94,1720.96 2445.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2445.94 1720.96 L2445.94 1720.96 L2446.22 1720.96 L2446.22 1720.96 L2445.94 1720.96 L2445.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2445.94,1720.96 2445.94,1720.96 2446.22,1720.96 2445.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2446.22 1720.96 L2446.22 1720.96 L2446.5 1720.96 L2446.5 1720.96 L2446.22 1720.96 L2446.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2446.22,1720.96 2446.22,1720.96 2446.5,1720.96 2446.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2446.5 1720.96 L2446.5 1720.96 L2446.78 1720.96 L2446.78 1720.96 L2446.5 1720.96 L2446.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2446.5,1720.96 2446.5,1720.96 2446.78,1720.96 2446.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2446.78 1720.96 L2446.78 1720.96 L2447.07 1720.96 L2447.07 1720.96 L2446.78 1720.96 L2446.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2446.78,1720.96 2446.78,1720.96 2447.07,1720.96 2446.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2447.07 1720.96 L2447.07 1720.96 L2447.35 1720.96 L2447.35 1720.96 L2447.07 1720.96 L2447.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2447.07,1720.96 2447.07,1720.96 2447.35,1720.96 2447.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2447.35 1720.96 L2447.35 1720.96 L2447.63 1720.96 L2447.63 1720.96 L2447.35 1720.96 L2447.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2447.35,1720.96 2447.35,1720.96 2447.63,1720.96 2447.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2447.63 1720.96 L2447.63 1720.96 L2447.91 1720.96 L2447.91 1720.96 L2447.63 1720.96 L2447.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2447.63,1720.96 2447.63,1720.96 2447.91,1720.96 2447.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2447.91 1720.96 L2447.91 1720.96 L2448.19 1720.96 L2448.19 1720.96 L2447.91 1720.96 L2447.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2447.91,1720.96 2447.91,1720.96 2448.19,1720.96 2447.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2448.19 1720.96 L2448.19 1720.96 L2448.48 1720.96 L2448.48 1720.96 L2448.19 1720.96 L2448.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2448.19,1720.96 2448.19,1720.96 2448.48,1720.96 2448.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2448.48 1720.96 L2448.48 1720.96 L2448.76 1720.96 L2448.76 1720.96 L2448.48 1720.96 L2448.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2448.48,1720.96 2448.48,1720.96 2448.76,1720.96 2448.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2448.76 1720.96 L2448.76 1720.96 L2449.04 1720.96 L2449.04 1720.96 L2448.76 1720.96 L2448.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2448.76,1720.96 2448.76,1720.96 2449.04,1720.96 2448.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2449.04 1720.96 L2449.04 1720.96 L2449.32 1720.96 L2449.32 1720.96 L2449.04 1720.96 L2449.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2449.04,1720.96 2449.04,1720.96 2449.32,1720.96 2449.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2449.32 1720.96 L2449.32 1720.96 L2449.6 1720.96 L2449.6 1720.96 L2449.32 1720.96 L2449.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2449.32,1720.96 2449.32,1720.96 2449.6,1720.96 2449.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2449.6 1720.96 L2449.6 1720.96 L2449.88 1720.96 L2449.88 1720.96 L2449.6 1720.96 L2449.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2449.6,1720.96 2449.6,1720.96 2449.88,1720.96 2449.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2449.88 1720.96 L2449.88 1720.96 L2450.17 1720.96 L2450.17 1720.96 L2449.88 1720.96 L2449.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2449.88,1720.96 2449.88,1720.96 2450.17,1720.96 2449.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2450.17 1720.96 L2450.17 1720.96 L2450.45 1720.96 L2450.45 1720.96 L2450.17 1720.96 L2450.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2450.17,1720.96 2450.17,1720.96 2450.45,1720.96 2450.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2450.45 1720.96 L2450.45 1720.96 L2450.73 1720.96 L2450.73 1720.96 L2450.45 1720.96 L2450.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2450.45,1720.96 2450.45,1720.96 2450.73,1720.96 2450.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2450.73 1720.96 L2450.73 1720.96 L2451.01 1720.96 L2451.01 1720.96 L2450.73 1720.96 L2450.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2450.73,1720.96 2450.73,1720.96 2451.01,1720.96 2450.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2451.01 1720.96 L2451.01 1720.96 L2451.29 1720.96 L2451.29 1720.96 L2451.01 1720.96 L2451.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2451.01,1720.96 2451.01,1720.96 2451.29,1720.96 2451.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2451.29 1720.96 L2451.29 1720.96 L2451.57 1720.96 L2451.57 1720.96 L2451.29 1720.96 L2451.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2451.29,1720.96 2451.29,1720.96 2451.57,1720.96 2451.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2451.57 1720.96 L2451.57 1720.96 L2451.86 1720.96 L2451.86 1720.96 L2451.57 1720.96 L2451.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2451.57,1720.96 2451.57,1720.96 2451.86,1720.96 2451.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2451.86 1720.96 L2451.86 1720.96 L2452.14 1720.96 L2452.14 1720.96 L2451.86 1720.96 L2451.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2451.86,1720.96 2451.86,1720.96 2452.14,1720.96 2451.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2452.14 1720.96 L2452.14 1720.96 L2452.42 1720.96 L2452.42 1720.96 L2452.14 1720.96 L2452.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2452.14,1720.96 2452.14,1720.96 2452.42,1720.96 2452.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2452.42 1720.96 L2452.42 1720.96 L2452.7 1720.96 L2452.7 1720.96 L2452.42 1720.96 L2452.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2452.42,1720.96 2452.42,1720.96 2452.7,1720.96 2452.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2452.7 1720.96 L2452.7 1720.96 L2452.98 1720.96 L2452.98 1720.96 L2452.7 1720.96 L2452.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2452.7,1720.96 2452.7,1720.96 2452.98,1720.96 2452.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2452.98 1720.96 L2452.98 1720.96 L2453.26 1720.96 L2453.26 1720.96 L2452.98 1720.96 L2452.98 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2452.98,1720.96 2452.98,1720.96 2453.26,1720.96 2452.98,1720.96 "/>
<path clip-path="url(#clip322)" d="M2453.26 1720.96 L2453.26 1720.96 L2453.55 1720.96 L2453.55 1720.96 L2453.26 1720.96 L2453.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2453.26,1720.96 2453.26,1720.96 2453.55,1720.96 2453.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2453.55 1720.96 L2453.55 1720.96 L2453.83 1720.96 L2453.83 1720.96 L2453.55 1720.96 L2453.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2453.55,1720.96 2453.55,1720.96 2453.83,1720.96 2453.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2453.83 1720.96 L2453.83 1720.96 L2454.11 1720.96 L2454.11 1720.96 L2453.83 1720.96 L2453.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2453.83,1720.96 2453.83,1720.96 2454.11,1720.96 2453.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2454.11 1720.96 L2454.11 1720.96 L2454.39 1720.96 L2454.39 1720.96 L2454.11 1720.96 L2454.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2454.11,1720.96 2454.11,1720.96 2454.39,1720.96 2454.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2454.39 1720.96 L2454.39 1720.96 L2454.67 1720.96 L2454.67 1720.96 L2454.39 1720.96 L2454.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2454.39,1720.96 2454.39,1720.96 2454.67,1720.96 2454.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2454.67 1720.96 L2454.67 1720.96 L2454.95 1720.96 L2454.95 1720.96 L2454.67 1720.96 L2454.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2454.67,1720.96 2454.67,1720.96 2454.95,1720.96 2454.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2454.95 1720.96 L2454.95 1720.96 L2455.24 1720.96 L2455.24 1720.96 L2454.95 1720.96 L2454.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2454.95,1720.96 2454.95,1720.96 2455.24,1720.96 2454.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2455.24 1720.96 L2455.24 1720.96 L2455.52 1720.96 L2455.52 1720.96 L2455.24 1720.96 L2455.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2455.24,1720.96 2455.24,1720.96 2455.52,1720.96 2455.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2455.52 1720.96 L2455.52 1720.96 L2455.8 1720.96 L2455.8 1720.96 L2455.52 1720.96 L2455.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2455.52,1720.96 2455.52,1720.96 2455.8,1720.96 2455.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2455.8 1720.96 L2455.8 1720.96 L2456.08 1720.96 L2456.08 1720.96 L2455.8 1720.96 L2455.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2455.8,1720.96 2455.8,1720.96 2456.08,1720.96 2455.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2456.08 1720.96 L2456.08 1720.96 L2456.36 1720.96 L2456.36 1720.96 L2456.08 1720.96 L2456.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2456.08,1720.96 2456.08,1720.96 2456.36,1720.96 2456.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2456.36 1720.96 L2456.36 1720.96 L2456.65 1720.96 L2456.65 1720.96 L2456.36 1720.96 L2456.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2456.36,1720.96 2456.36,1720.96 2456.65,1720.96 2456.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2456.65 1720.96 L2456.65 1720.96 L2456.93 1720.96 L2456.93 1720.96 L2456.65 1720.96 L2456.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2456.65,1720.96 2456.65,1720.96 2456.93,1720.96 2456.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2456.93 1720.96 L2456.93 1720.96 L2457.21 1720.96 L2457.21 1720.96 L2456.93 1720.96 L2456.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2456.93,1720.96 2456.93,1720.96 2457.21,1720.96 2456.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2457.21 1720.96 L2457.21 1720.96 L2457.49 1720.96 L2457.49 1720.96 L2457.21 1720.96 L2457.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2457.21,1720.96 2457.21,1720.96 2457.49,1720.96 2457.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2457.49 1720.96 L2457.49 1720.96 L2457.77 1720.96 L2457.77 1720.96 L2457.49 1720.96 L2457.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2457.49,1720.96 2457.49,1720.96 2457.77,1720.96 2457.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2457.77 1720.96 L2457.77 1720.96 L2458.05 1720.96 L2458.05 1720.96 L2457.77 1720.96 L2457.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2457.77,1720.96 2457.77,1720.96 2458.05,1720.96 2457.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2458.05 1720.96 L2458.05 1720.96 L2458.34 1720.96 L2458.34 1720.96 L2458.05 1720.96 L2458.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2458.05,1720.96 2458.05,1720.96 2458.34,1720.96 2458.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2458.34 1720.96 L2458.34 1720.96 L2458.62 1720.96 L2458.62 1720.96 L2458.34 1720.96 L2458.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2458.34,1720.96 2458.34,1720.96 2458.62,1720.96 2458.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2458.62 1720.96 L2458.62 1720.96 L2458.9 1720.96 L2458.9 1720.96 L2458.62 1720.96 L2458.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2458.62,1720.96 2458.62,1720.96 2458.9,1720.96 2458.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2458.9 1720.96 L2458.9 1720.96 L2459.18 1720.96 L2459.18 1720.96 L2458.9 1720.96 L2458.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2458.9,1720.96 2458.9,1720.96 2459.18,1720.96 2458.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2459.18 1720.96 L2459.18 1720.96 L2459.46 1720.96 L2459.46 1720.96 L2459.18 1720.96 L2459.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2459.18,1720.96 2459.18,1720.96 2459.46,1720.96 2459.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2459.46 1720.96 L2459.46 1720.96 L2459.74 1720.96 L2459.74 1720.96 L2459.46 1720.96 L2459.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2459.46,1720.96 2459.46,1720.96 2459.74,1720.96 2459.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2459.74 1720.96 L2459.74 1720.96 L2460.03 1720.96 L2460.03 1720.96 L2459.74 1720.96 L2459.74 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2459.74,1720.96 2459.74,1720.96 2460.03,1720.96 2459.74,1720.96 "/>
<path clip-path="url(#clip322)" d="M2460.03 1720.96 L2460.03 1720.96 L2460.31 1720.96 L2460.31 1720.96 L2460.03 1720.96 L2460.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2460.03,1720.96 2460.03,1720.96 2460.31,1720.96 2460.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2460.31 1720.96 L2460.31 1720.96 L2460.59 1720.96 L2460.59 1720.96 L2460.31 1720.96 L2460.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2460.31,1720.96 2460.31,1720.96 2460.59,1720.96 2460.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2460.59 1720.96 L2460.59 1720.96 L2460.87 1720.96 L2460.87 1720.96 L2460.59 1720.96 L2460.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2460.59,1720.96 2460.59,1720.96 2460.87,1720.96 2460.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2460.87 1720.96 L2460.87 1720.96 L2461.15 1720.96 L2461.15 1720.96 L2460.87 1720.96 L2460.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2460.87,1720.96 2460.87,1720.96 2461.15,1720.96 2460.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2461.15 1720.96 L2461.15 1720.96 L2461.43 1720.96 L2461.43 1720.96 L2461.15 1720.96 L2461.15 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2461.15,1720.96 2461.15,1720.96 2461.43,1720.96 2461.15,1720.96 "/>
<path clip-path="url(#clip322)" d="M2461.43 1720.96 L2461.43 1720.96 L2461.72 1720.96 L2461.72 1720.96 L2461.43 1720.96 L2461.43 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2461.43,1720.96 2461.43,1720.96 2461.72,1720.96 2461.43,1720.96 "/>
<path clip-path="url(#clip322)" d="M2461.72 1720.96 L2461.72 1720.96 L2462 1720.96 L2462 1720.96 L2461.72 1720.96 L2461.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2461.72,1720.96 2461.72,1720.96 2462,1720.96 2461.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2462 1720.96 L2462 1720.96 L2462.28 1720.96 L2462.28 1720.96 L2462 1720.96 L2462 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2462,1720.96 2462,1720.96 2462.28,1720.96 2462,1720.96 "/>
<path clip-path="url(#clip322)" d="M2462.28 1720.96 L2462.28 1720.96 L2462.56 1720.96 L2462.56 1720.96 L2462.28 1720.96 L2462.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2462.28,1720.96 2462.28,1720.96 2462.56,1720.96 2462.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2462.56 1720.96 L2462.56 1720.96 L2462.84 1720.96 L2462.84 1720.96 L2462.56 1720.96 L2462.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2462.56,1720.96 2462.56,1720.96 2462.84,1720.96 2462.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2462.84 1720.96 L2462.84 1720.96 L2463.12 1720.96 L2463.12 1720.96 L2462.84 1720.96 L2462.84 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2462.84,1720.96 2462.84,1720.96 2463.12,1720.96 2462.84,1720.96 "/>
<path clip-path="url(#clip322)" d="M2463.12 1720.96 L2463.12 1720.96 L2463.41 1720.96 L2463.41 1720.96 L2463.12 1720.96 L2463.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2463.12,1720.96 2463.12,1720.96 2463.41,1720.96 2463.12,1720.96 "/>
<path clip-path="url(#clip322)" d="M2463.41 1720.96 L2463.41 1720.96 L2463.69 1720.96 L2463.69 1720.96 L2463.41 1720.96 L2463.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2463.41,1720.96 2463.41,1720.96 2463.69,1720.96 2463.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2463.69 1720.96 L2463.69 1720.96 L2463.97 1720.96 L2463.97 1720.96 L2463.69 1720.96 L2463.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2463.69,1720.96 2463.69,1720.96 2463.97,1720.96 2463.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2463.97 1720.96 L2463.97 1720.96 L2464.25 1720.96 L2464.25 1720.96 L2463.97 1720.96 L2463.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2463.97,1720.96 2463.97,1720.96 2464.25,1720.96 2463.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2464.25 1720.96 L2464.25 1720.96 L2464.53 1720.96 L2464.53 1720.96 L2464.25 1720.96 L2464.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2464.25,1720.96 2464.25,1720.96 2464.53,1720.96 2464.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2464.53 1720.96 L2464.53 1720.96 L2464.82 1720.96 L2464.82 1720.96 L2464.53 1720.96 L2464.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2464.53,1720.96 2464.53,1720.96 2464.82,1720.96 2464.53,1720.96 "/>
<path clip-path="url(#clip322)" d="M2464.82 1720.96 L2464.82 1720.96 L2465.1 1720.96 L2465.1 1720.96 L2464.82 1720.96 L2464.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2464.82,1720.96 2464.82,1720.96 2465.1,1720.96 2464.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2465.1 1720.96 L2465.1 1720.96 L2465.38 1720.96 L2465.38 1720.96 L2465.1 1720.96 L2465.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2465.1,1720.96 2465.1,1720.96 2465.38,1720.96 2465.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2465.38 1720.96 L2465.38 1720.96 L2465.66 1720.96 L2465.66 1720.96 L2465.38 1720.96 L2465.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2465.38,1720.96 2465.38,1720.96 2465.66,1720.96 2465.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2465.66 1720.96 L2465.66 1720.96 L2465.94 1720.96 L2465.94 1720.96 L2465.66 1720.96 L2465.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2465.66,1720.96 2465.66,1720.96 2465.94,1720.96 2465.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2465.94 1720.96 L2465.94 1720.96 L2466.22 1720.96 L2466.22 1720.96 L2465.94 1720.96 L2465.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2465.94,1720.96 2465.94,1720.96 2466.22,1720.96 2465.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2466.22 1720.96 L2466.22 1720.96 L2466.51 1720.96 L2466.51 1720.96 L2466.22 1720.96 L2466.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2466.22,1720.96 2466.22,1720.96 2466.51,1720.96 2466.22,1720.96 "/>
<path clip-path="url(#clip322)" d="M2466.51 1720.96 L2466.51 1720.96 L2466.79 1720.96 L2466.79 1720.96 L2466.51 1720.96 L2466.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2466.51,1720.96 2466.51,1720.96 2466.79,1720.96 2466.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2466.79 1720.96 L2466.79 1720.96 L2467.07 1720.96 L2467.07 1720.96 L2466.79 1720.96 L2466.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2466.79,1720.96 2466.79,1720.96 2467.07,1720.96 2466.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2467.07 1720.96 L2467.07 1720.96 L2467.35 1720.96 L2467.35 1720.96 L2467.07 1720.96 L2467.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2467.07,1720.96 2467.07,1720.96 2467.35,1720.96 2467.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2467.35 1720.96 L2467.35 1720.96 L2467.63 1720.96 L2467.63 1720.96 L2467.35 1720.96 L2467.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2467.35,1720.96 2467.35,1720.96 2467.63,1720.96 2467.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2467.63 1720.96 L2467.63 1720.96 L2467.91 1720.96 L2467.91 1720.96 L2467.63 1720.96 L2467.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2467.63,1720.96 2467.63,1720.96 2467.91,1720.96 2467.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2467.91 1720.96 L2467.91 1720.96 L2468.2 1720.96 L2468.2 1720.96 L2467.91 1720.96 L2467.91 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2467.91,1720.96 2467.91,1720.96 2468.2,1720.96 2467.91,1720.96 "/>
<path clip-path="url(#clip322)" d="M2468.2 1720.96 L2468.2 1720.96 L2468.48 1720.96 L2468.48 1720.96 L2468.2 1720.96 L2468.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2468.2,1720.96 2468.2,1720.96 2468.48,1720.96 2468.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2468.48 1720.96 L2468.48 1720.96 L2468.76 1720.96 L2468.76 1720.96 L2468.48 1720.96 L2468.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2468.48,1720.96 2468.48,1720.96 2468.76,1720.96 2468.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2468.76 1720.96 L2468.76 1720.96 L2469.04 1720.96 L2469.04 1720.96 L2468.76 1720.96 L2468.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2468.76,1720.96 2468.76,1720.96 2469.04,1720.96 2468.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2469.04 1720.96 L2469.04 1720.96 L2469.32 1720.96 L2469.32 1720.96 L2469.04 1720.96 L2469.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2469.04,1720.96 2469.04,1720.96 2469.32,1720.96 2469.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2469.32 1720.96 L2469.32 1720.96 L2469.6 1720.96 L2469.6 1720.96 L2469.32 1720.96 L2469.32 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2469.32,1720.96 2469.32,1720.96 2469.6,1720.96 2469.32,1720.96 "/>
<path clip-path="url(#clip322)" d="M2469.6 1720.96 L2469.6 1720.96 L2469.89 1720.96 L2469.89 1720.96 L2469.6 1720.96 L2469.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2469.6,1720.96 2469.6,1720.96 2469.89,1720.96 2469.6,1720.96 "/>
<path clip-path="url(#clip322)" d="M2469.89 1720.96 L2469.89 1720.96 L2470.17 1720.96 L2470.17 1720.96 L2469.89 1720.96 L2469.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2469.89,1720.96 2469.89,1720.96 2470.17,1720.96 2469.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2470.17 1720.96 L2470.17 1720.96 L2470.45 1720.96 L2470.45 1720.96 L2470.17 1720.96 L2470.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2470.17,1720.96 2470.17,1720.96 2470.45,1720.96 2470.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2470.45 1720.96 L2470.45 1720.96 L2470.73 1720.96 L2470.73 1720.96 L2470.45 1720.96 L2470.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2470.45,1720.96 2470.45,1720.96 2470.73,1720.96 2470.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2470.73 1720.96 L2470.73 1720.96 L2471.01 1720.96 L2471.01 1720.96 L2470.73 1720.96 L2470.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2470.73,1720.96 2470.73,1720.96 2471.01,1720.96 2470.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2471.01 1720.96 L2471.01 1720.96 L2471.29 1720.96 L2471.29 1720.96 L2471.01 1720.96 L2471.01 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2471.01,1720.96 2471.01,1720.96 2471.29,1720.96 2471.01,1720.96 "/>
<path clip-path="url(#clip322)" d="M2471.29 1720.96 L2471.29 1720.96 L2471.58 1720.96 L2471.58 1720.96 L2471.29 1720.96 L2471.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2471.29,1720.96 2471.29,1720.96 2471.58,1720.96 2471.29,1720.96 "/>
<path clip-path="url(#clip322)" d="M2471.58 1720.96 L2471.58 1720.96 L2471.86 1720.96 L2471.86 1720.96 L2471.58 1720.96 L2471.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2471.58,1720.96 2471.58,1720.96 2471.86,1720.96 2471.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2471.86 1720.96 L2471.86 1720.96 L2472.14 1720.96 L2472.14 1720.96 L2471.86 1720.96 L2471.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2471.86,1720.96 2471.86,1720.96 2472.14,1720.96 2471.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2472.14 1720.96 L2472.14 1720.96 L2472.42 1720.96 L2472.42 1720.96 L2472.14 1720.96 L2472.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2472.14,1720.96 2472.14,1720.96 2472.42,1720.96 2472.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2472.42 1720.96 L2472.42 1720.96 L2472.7 1720.96 L2472.7 1720.96 L2472.42 1720.96 L2472.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2472.42,1720.96 2472.42,1720.96 2472.7,1720.96 2472.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2472.7 1720.96 L2472.7 1720.96 L2472.99 1720.96 L2472.99 1720.96 L2472.7 1720.96 L2472.7 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2472.7,1720.96 2472.7,1720.96 2472.99,1720.96 2472.7,1720.96 "/>
<path clip-path="url(#clip322)" d="M2472.99 1720.96 L2472.99 1720.96 L2473.27 1720.96 L2473.27 1720.96 L2472.99 1720.96 L2472.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2472.99,1720.96 2472.99,1720.96 2473.27,1720.96 2472.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2473.27 1720.96 L2473.27 1720.96 L2473.55 1720.96 L2473.55 1720.96 L2473.27 1720.96 L2473.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2473.27,1720.96 2473.27,1720.96 2473.55,1720.96 2473.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2473.55 1720.96 L2473.55 1720.96 L2473.83 1720.96 L2473.83 1720.96 L2473.55 1720.96 L2473.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2473.55,1720.96 2473.55,1720.96 2473.83,1720.96 2473.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2473.83 1720.96 L2473.83 1720.96 L2474.11 1720.96 L2474.11 1720.96 L2473.83 1720.96 L2473.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2473.83,1720.96 2473.83,1720.96 2474.11,1720.96 2473.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2474.11 1720.96 L2474.11 1720.96 L2474.39 1720.96 L2474.39 1720.96 L2474.11 1720.96 L2474.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2474.11,1720.96 2474.11,1720.96 2474.39,1720.96 2474.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2474.39 1720.96 L2474.39 1720.96 L2474.68 1720.96 L2474.68 1720.96 L2474.39 1720.96 L2474.39 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2474.39,1720.96 2474.39,1720.96 2474.68,1720.96 2474.39,1720.96 "/>
<path clip-path="url(#clip322)" d="M2474.68 1720.96 L2474.68 1720.96 L2474.96 1720.96 L2474.96 1720.96 L2474.68 1720.96 L2474.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2474.68,1720.96 2474.68,1720.96 2474.96,1720.96 2474.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2474.96 1720.96 L2474.96 1720.96 L2475.24 1720.96 L2475.24 1720.96 L2474.96 1720.96 L2474.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2474.96,1720.96 2474.96,1720.96 2475.24,1720.96 2474.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2475.24 1720.96 L2475.24 1720.96 L2475.52 1720.96 L2475.52 1720.96 L2475.24 1720.96 L2475.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2475.24,1720.96 2475.24,1720.96 2475.52,1720.96 2475.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2475.52 1720.96 L2475.52 1720.96 L2475.8 1720.96 L2475.8 1720.96 L2475.52 1720.96 L2475.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2475.52,1720.96 2475.52,1720.96 2475.8,1720.96 2475.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2475.8 1720.96 L2475.8 1720.96 L2476.08 1720.96 L2476.08 1720.96 L2475.8 1720.96 L2475.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2475.8,1720.96 2475.8,1720.96 2476.08,1720.96 2475.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2476.08 1720.96 L2476.08 1720.96 L2476.37 1720.96 L2476.37 1720.96 L2476.08 1720.96 L2476.08 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2476.08,1720.96 2476.08,1720.96 2476.37,1720.96 2476.08,1720.96 "/>
<path clip-path="url(#clip322)" d="M2476.37 1720.96 L2476.37 1720.96 L2476.65 1720.96 L2476.65 1720.96 L2476.37 1720.96 L2476.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2476.37,1720.96 2476.37,1720.96 2476.65,1720.96 2476.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2476.65 1720.96 L2476.65 1720.96 L2476.93 1720.96 L2476.93 1720.96 L2476.65 1720.96 L2476.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2476.65,1720.96 2476.65,1720.96 2476.93,1720.96 2476.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2476.93 1720.96 L2476.93 1720.96 L2477.21 1720.96 L2477.21 1720.96 L2476.93 1720.96 L2476.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2476.93,1720.96 2476.93,1720.96 2477.21,1720.96 2476.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2477.21 1720.96 L2477.21 1720.96 L2477.49 1720.96 L2477.49 1720.96 L2477.21 1720.96 L2477.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2477.21,1720.96 2477.21,1720.96 2477.49,1720.96 2477.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2477.49 1720.96 L2477.49 1720.96 L2477.77 1720.96 L2477.77 1720.96 L2477.49 1720.96 L2477.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2477.49,1720.96 2477.49,1720.96 2477.77,1720.96 2477.49,1720.96 "/>
<path clip-path="url(#clip322)" d="M2477.77 1720.96 L2477.77 1720.96 L2478.06 1720.96 L2478.06 1720.96 L2477.77 1720.96 L2477.77 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2477.77,1720.96 2477.77,1720.96 2478.06,1720.96 2477.77,1720.96 "/>
<path clip-path="url(#clip322)" d="M2478.06 1720.96 L2478.06 1720.96 L2478.34 1720.96 L2478.34 1720.96 L2478.06 1720.96 L2478.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2478.06,1720.96 2478.06,1720.96 2478.34,1720.96 2478.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2478.34 1720.96 L2478.34 1720.96 L2478.62 1720.96 L2478.62 1720.96 L2478.34 1720.96 L2478.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2478.34,1720.96 2478.34,1720.96 2478.62,1720.96 2478.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2478.62 1720.96 L2478.62 1720.96 L2478.9 1720.96 L2478.9 1720.96 L2478.62 1720.96 L2478.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2478.62,1720.96 2478.62,1720.96 2478.9,1720.96 2478.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2478.9 1720.96 L2478.9 1720.96 L2479.18 1720.96 L2479.18 1720.96 L2478.9 1720.96 L2478.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2478.9,1720.96 2478.9,1720.96 2479.18,1720.96 2478.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2479.18 1720.96 L2479.18 1720.96 L2479.46 1720.96 L2479.46 1720.96 L2479.18 1720.96 L2479.18 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2479.18,1720.96 2479.18,1720.96 2479.46,1720.96 2479.18,1720.96 "/>
<path clip-path="url(#clip322)" d="M2479.46 1720.96 L2479.46 1720.96 L2479.75 1720.96 L2479.75 1720.96 L2479.46 1720.96 L2479.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2479.46,1720.96 2479.46,1720.96 2479.75,1720.96 2479.46,1720.96 "/>
<path clip-path="url(#clip322)" d="M2479.75 1720.96 L2479.75 1720.96 L2480.03 1720.96 L2480.03 1720.96 L2479.75 1720.96 L2479.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2479.75,1720.96 2479.75,1720.96 2480.03,1720.96 2479.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2480.03 1720.96 L2480.03 1720.96 L2480.31 1720.96 L2480.31 1720.96 L2480.03 1720.96 L2480.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2480.03,1720.96 2480.03,1720.96 2480.31,1720.96 2480.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2480.31 1720.96 L2480.31 1720.96 L2480.59 1720.96 L2480.59 1720.96 L2480.31 1720.96 L2480.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2480.31,1720.96 2480.31,1720.96 2480.59,1720.96 2480.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2480.59 1720.96 L2480.59 1720.96 L2480.87 1720.96 L2480.87 1720.96 L2480.59 1720.96 L2480.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2480.59,1720.96 2480.59,1720.96 2480.87,1720.96 2480.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2480.87 1720.96 L2480.87 1720.96 L2481.16 1720.96 L2481.16 1720.96 L2480.87 1720.96 L2480.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2480.87,1720.96 2480.87,1720.96 2481.16,1720.96 2480.87,1720.96 "/>
<path clip-path="url(#clip322)" d="M2481.16 1720.96 L2481.16 1720.96 L2481.44 1720.96 L2481.44 1720.96 L2481.16 1720.96 L2481.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2481.16,1720.96 2481.16,1720.96 2481.44,1720.96 2481.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2481.44 1720.96 L2481.44 1720.96 L2481.72 1720.96 L2481.72 1720.96 L2481.44 1720.96 L2481.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2481.44,1720.96 2481.44,1720.96 2481.72,1720.96 2481.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2481.72 1720.96 L2481.72 1720.96 L2482 1720.96 L2482 1720.96 L2481.72 1720.96 L2481.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2481.72,1720.96 2481.72,1720.96 2482,1720.96 2481.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2482 1720.96 L2482 1720.96 L2482.28 1720.96 L2482.28 1720.96 L2482 1720.96 L2482 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2482,1720.96 2482,1720.96 2482.28,1720.96 2482,1720.96 "/>
<path clip-path="url(#clip322)" d="M2482.28 1720.96 L2482.28 1720.96 L2482.56 1720.96 L2482.56 1720.96 L2482.28 1720.96 L2482.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2482.28,1720.96 2482.28,1720.96 2482.56,1720.96 2482.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2482.56 1720.96 L2482.56 1720.96 L2482.85 1720.96 L2482.85 1720.96 L2482.56 1720.96 L2482.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2482.56,1720.96 2482.56,1720.96 2482.85,1720.96 2482.56,1720.96 "/>
<path clip-path="url(#clip322)" d="M2482.85 1720.96 L2482.85 1720.96 L2483.13 1720.96 L2483.13 1720.96 L2482.85 1720.96 L2482.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2482.85,1720.96 2482.85,1720.96 2483.13,1720.96 2482.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2483.13 1720.96 L2483.13 1720.96 L2483.41 1720.96 L2483.41 1720.96 L2483.13 1720.96 L2483.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2483.13,1720.96 2483.13,1720.96 2483.41,1720.96 2483.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2483.41 1720.96 L2483.41 1720.96 L2483.69 1720.96 L2483.69 1720.96 L2483.41 1720.96 L2483.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2483.41,1720.96 2483.41,1720.96 2483.69,1720.96 2483.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2483.69 1720.96 L2483.69 1720.96 L2483.97 1720.96 L2483.97 1720.96 L2483.69 1720.96 L2483.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2483.69,1720.96 2483.69,1720.96 2483.97,1720.96 2483.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2483.97 1720.96 L2483.97 1720.96 L2484.25 1720.96 L2484.25 1720.96 L2483.97 1720.96 L2483.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2483.97,1720.96 2483.97,1720.96 2484.25,1720.96 2483.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2484.25 1720.96 L2484.25 1720.96 L2484.54 1720.96 L2484.54 1720.96 L2484.25 1720.96 L2484.25 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2484.25,1720.96 2484.25,1720.96 2484.54,1720.96 2484.25,1720.96 "/>
<path clip-path="url(#clip322)" d="M2484.54 1720.96 L2484.54 1720.96 L2484.82 1720.96 L2484.82 1720.96 L2484.54 1720.96 L2484.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2484.54,1720.96 2484.54,1720.96 2484.82,1720.96 2484.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2484.82 1720.96 L2484.82 1720.96 L2485.1 1720.96 L2485.1 1720.96 L2484.82 1720.96 L2484.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2484.82,1720.96 2484.82,1720.96 2485.1,1720.96 2484.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2485.1 1720.96 L2485.1 1720.96 L2485.38 1720.96 L2485.38 1720.96 L2485.1 1720.96 L2485.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2485.1,1720.96 2485.1,1720.96 2485.38,1720.96 2485.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2485.38 1720.96 L2485.38 1720.96 L2485.66 1720.96 L2485.66 1720.96 L2485.38 1720.96 L2485.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2485.38,1720.96 2485.38,1720.96 2485.66,1720.96 2485.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2485.66 1720.96 L2485.66 1720.96 L2485.94 1720.96 L2485.94 1720.96 L2485.66 1720.96 L2485.66 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2485.66,1720.96 2485.66,1720.96 2485.94,1720.96 2485.66,1720.96 "/>
<path clip-path="url(#clip322)" d="M2485.94 1720.96 L2485.94 1720.96 L2486.23 1720.96 L2486.23 1720.96 L2485.94 1720.96 L2485.94 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2485.94,1720.96 2485.94,1720.96 2486.23,1720.96 2485.94,1720.96 "/>
<path clip-path="url(#clip322)" d="M2486.23 1720.96 L2486.23 1720.96 L2486.51 1720.96 L2486.51 1720.96 L2486.23 1720.96 L2486.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2486.23,1720.96 2486.23,1720.96 2486.51,1720.96 2486.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2486.51 1720.96 L2486.51 1720.96 L2486.79 1720.96 L2486.79 1720.96 L2486.51 1720.96 L2486.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2486.51,1720.96 2486.51,1720.96 2486.79,1720.96 2486.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2486.79 1720.96 L2486.79 1720.96 L2487.07 1720.96 L2487.07 1720.96 L2486.79 1720.96 L2486.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2486.79,1720.96 2486.79,1720.96 2487.07,1720.96 2486.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2487.07 1720.96 L2487.07 1720.96 L2487.35 1720.96 L2487.35 1720.96 L2487.07 1720.96 L2487.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2487.07,1720.96 2487.07,1720.96 2487.35,1720.96 2487.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2487.35 1720.96 L2487.35 1720.96 L2487.63 1720.96 L2487.63 1720.96 L2487.35 1720.96 L2487.35 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2487.35,1720.96 2487.35,1720.96 2487.63,1720.96 2487.35,1720.96 "/>
<path clip-path="url(#clip322)" d="M2487.63 1720.96 L2487.63 1720.96 L2487.92 1720.96 L2487.92 1720.96 L2487.63 1720.96 L2487.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2487.63,1720.96 2487.63,1720.96 2487.92,1720.96 2487.63,1720.96 "/>
<path clip-path="url(#clip322)" d="M2487.92 1720.96 L2487.92 1720.96 L2488.2 1720.96 L2488.2 1720.96 L2487.92 1720.96 L2487.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2487.92,1720.96 2487.92,1720.96 2488.2,1720.96 2487.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2488.2 1720.96 L2488.2 1720.96 L2488.48 1720.96 L2488.48 1720.96 L2488.2 1720.96 L2488.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2488.2,1720.96 2488.2,1720.96 2488.48,1720.96 2488.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2488.48 1720.96 L2488.48 1720.96 L2488.76 1720.96 L2488.76 1720.96 L2488.48 1720.96 L2488.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2488.48,1720.96 2488.48,1720.96 2488.76,1720.96 2488.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2488.76 1720.96 L2488.76 1720.96 L2489.04 1720.96 L2489.04 1720.96 L2488.76 1720.96 L2488.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2488.76,1720.96 2488.76,1720.96 2489.04,1720.96 2488.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2489.04 1720.96 L2489.04 1720.96 L2489.33 1720.96 L2489.33 1720.96 L2489.04 1720.96 L2489.04 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2489.04,1720.96 2489.04,1720.96 2489.33,1720.96 2489.04,1720.96 "/>
<path clip-path="url(#clip322)" d="M2489.33 1720.96 L2489.33 1720.96 L2489.61 1720.96 L2489.61 1720.96 L2489.33 1720.96 L2489.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2489.33,1720.96 2489.33,1720.96 2489.61,1720.96 2489.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2489.61 1720.96 L2489.61 1720.96 L2489.89 1720.96 L2489.89 1720.96 L2489.61 1720.96 L2489.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2489.61,1720.96 2489.61,1720.96 2489.89,1720.96 2489.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2489.89 1720.96 L2489.89 1720.96 L2490.17 1720.96 L2490.17 1720.96 L2489.89 1720.96 L2489.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2489.89,1720.96 2489.89,1720.96 2490.17,1720.96 2489.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2490.17 1720.96 L2490.17 1720.96 L2490.45 1720.96 L2490.45 1720.96 L2490.17 1720.96 L2490.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2490.17,1720.96 2490.17,1720.96 2490.45,1720.96 2490.17,1720.96 "/>
<path clip-path="url(#clip322)" d="M2490.45 1720.96 L2490.45 1720.96 L2490.73 1720.96 L2490.73 1720.96 L2490.45 1720.96 L2490.45 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2490.45,1720.96 2490.45,1720.96 2490.73,1720.96 2490.45,1720.96 "/>
<path clip-path="url(#clip322)" d="M2490.73 1720.96 L2490.73 1720.96 L2491.02 1720.96 L2491.02 1720.96 L2490.73 1720.96 L2490.73 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2490.73,1720.96 2490.73,1720.96 2491.02,1720.96 2490.73,1720.96 "/>
<path clip-path="url(#clip322)" d="M2491.02 1720.96 L2491.02 1720.96 L2491.3 1720.96 L2491.3 1720.96 L2491.02 1720.96 L2491.02 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2491.02,1720.96 2491.02,1720.96 2491.3,1720.96 2491.02,1720.96 "/>
<path clip-path="url(#clip322)" d="M2491.3 1720.96 L2491.3 1720.96 L2491.58 1720.96 L2491.58 1720.96 L2491.3 1720.96 L2491.3 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2491.3,1720.96 2491.3,1720.96 2491.58,1720.96 2491.3,1720.96 "/>
<path clip-path="url(#clip322)" d="M2491.58 1720.96 L2491.58 1720.96 L2491.86 1720.96 L2491.86 1720.96 L2491.58 1720.96 L2491.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2491.58,1720.96 2491.58,1720.96 2491.86,1720.96 2491.58,1720.96 "/>
<path clip-path="url(#clip322)" d="M2491.86 1720.96 L2491.86 1720.96 L2492.14 1720.96 L2492.14 1720.96 L2491.86 1720.96 L2491.86 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2491.86,1720.96 2491.86,1720.96 2492.14,1720.96 2491.86,1720.96 "/>
<path clip-path="url(#clip322)" d="M2492.14 1720.96 L2492.14 1720.96 L2492.42 1720.96 L2492.42 1720.96 L2492.14 1720.96 L2492.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2492.14,1720.96 2492.14,1720.96 2492.42,1720.96 2492.14,1720.96 "/>
<path clip-path="url(#clip322)" d="M2492.42 1720.96 L2492.42 1720.96 L2492.71 1720.96 L2492.71 1720.96 L2492.42 1720.96 L2492.42 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2492.42,1720.96 2492.42,1720.96 2492.71,1720.96 2492.42,1720.96 "/>
<path clip-path="url(#clip322)" d="M2492.71 1720.96 L2492.71 1720.96 L2492.99 1720.96 L2492.99 1720.96 L2492.71 1720.96 L2492.71 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2492.71,1720.96 2492.71,1720.96 2492.99,1720.96 2492.71,1720.96 "/>
<path clip-path="url(#clip322)" d="M2492.99 1720.96 L2492.99 1720.96 L2493.27 1720.96 L2493.27 1720.96 L2492.99 1720.96 L2492.99 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2492.99,1720.96 2492.99,1720.96 2493.27,1720.96 2492.99,1720.96 "/>
<path clip-path="url(#clip322)" d="M2493.27 1720.96 L2493.27 1720.96 L2493.55 1720.96 L2493.55 1720.96 L2493.27 1720.96 L2493.27 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2493.27,1720.96 2493.27,1720.96 2493.55,1720.96 2493.27,1720.96 "/>
<path clip-path="url(#clip322)" d="M2493.55 1720.96 L2493.55 1720.96 L2493.83 1720.96 L2493.83 1720.96 L2493.55 1720.96 L2493.55 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2493.55,1720.96 2493.55,1720.96 2493.83,1720.96 2493.55,1720.96 "/>
<path clip-path="url(#clip322)" d="M2493.83 1720.96 L2493.83 1720.96 L2494.11 1720.96 L2494.11 1720.96 L2493.83 1720.96 L2493.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2493.83,1720.96 2493.83,1720.96 2494.11,1720.96 2493.83,1720.96 "/>
<path clip-path="url(#clip322)" d="M2494.11 1720.96 L2494.11 1720.96 L2494.4 1720.96 L2494.4 1720.96 L2494.11 1720.96 L2494.11 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2494.11,1720.96 2494.11,1720.96 2494.4,1720.96 2494.11,1720.96 "/>
<path clip-path="url(#clip322)" d="M2494.4 1720.96 L2494.4 1720.96 L2494.68 1720.96 L2494.68 1720.96 L2494.4 1720.96 L2494.4 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2494.4,1720.96 2494.4,1720.96 2494.68,1720.96 2494.4,1720.96 "/>
<path clip-path="url(#clip322)" d="M2494.68 1720.96 L2494.68 1720.96 L2494.96 1720.96 L2494.96 1720.96 L2494.68 1720.96 L2494.68 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2494.68,1720.96 2494.68,1720.96 2494.96,1720.96 2494.68,1720.96 "/>
<path clip-path="url(#clip322)" d="M2494.96 1720.96 L2494.96 1720.96 L2495.24 1720.96 L2495.24 1720.96 L2494.96 1720.96 L2494.96 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2494.96,1720.96 2494.96,1720.96 2495.24,1720.96 2494.96,1720.96 "/>
<path clip-path="url(#clip322)" d="M2495.24 1720.96 L2495.24 1720.96 L2495.52 1720.96 L2495.52 1720.96 L2495.24 1720.96 L2495.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2495.24,1720.96 2495.24,1720.96 2495.52,1720.96 2495.24,1720.96 "/>
<path clip-path="url(#clip322)" d="M2495.52 1720.96 L2495.52 1720.96 L2495.8 1720.96 L2495.8 1720.96 L2495.52 1720.96 L2495.52 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2495.52,1720.96 2495.52,1720.96 2495.8,1720.96 2495.52,1720.96 "/>
<path clip-path="url(#clip322)" d="M2495.8 1720.96 L2495.8 1720.96 L2496.09 1720.96 L2496.09 1720.96 L2495.8 1720.96 L2495.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2495.8,1720.96 2495.8,1720.96 2496.09,1720.96 2495.8,1720.96 "/>
<path clip-path="url(#clip322)" d="M2496.09 1720.96 L2496.09 1720.96 L2496.37 1720.96 L2496.37 1720.96 L2496.09 1720.96 L2496.09 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2496.09,1720.96 2496.09,1720.96 2496.37,1720.96 2496.09,1720.96 "/>
<path clip-path="url(#clip322)" d="M2496.37 1720.96 L2496.37 1720.96 L2496.65 1720.96 L2496.65 1720.96 L2496.37 1720.96 L2496.37 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2496.37,1720.96 2496.37,1720.96 2496.65,1720.96 2496.37,1720.96 "/>
<path clip-path="url(#clip322)" d="M2496.65 1720.96 L2496.65 1720.96 L2496.93 1720.96 L2496.93 1720.96 L2496.65 1720.96 L2496.65 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2496.65,1720.96 2496.65,1720.96 2496.93,1720.96 2496.65,1720.96 "/>
<path clip-path="url(#clip322)" d="M2496.93 1720.96 L2496.93 1720.96 L2497.21 1720.96 L2497.21 1720.96 L2496.93 1720.96 L2496.93 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2496.93,1720.96 2496.93,1720.96 2497.21,1720.96 2496.93,1720.96 "/>
<path clip-path="url(#clip322)" d="M2497.21 1720.96 L2497.21 1720.96 L2497.5 1720.96 L2497.5 1720.96 L2497.21 1720.96 L2497.21 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2497.21,1720.96 2497.21,1720.96 2497.5,1720.96 2497.21,1720.96 "/>
<path clip-path="url(#clip322)" d="M2497.5 1720.96 L2497.5 1720.96 L2497.78 1720.96 L2497.78 1720.96 L2497.5 1720.96 L2497.5 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2497.5,1720.96 2497.5,1720.96 2497.78,1720.96 2497.5,1720.96 "/>
<path clip-path="url(#clip322)" d="M2497.78 1720.96 L2497.78 1720.96 L2498.06 1720.96 L2498.06 1720.96 L2497.78 1720.96 L2497.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2497.78,1720.96 2497.78,1720.96 2498.06,1720.96 2497.78,1720.96 "/>
<path clip-path="url(#clip322)" d="M2498.06 1720.96 L2498.06 1720.96 L2498.34 1720.96 L2498.34 1720.96 L2498.06 1720.96 L2498.06 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2498.06,1720.96 2498.06,1720.96 2498.34,1720.96 2498.06,1720.96 "/>
<path clip-path="url(#clip322)" d="M2498.34 1720.96 L2498.34 1720.96 L2498.62 1720.96 L2498.62 1720.96 L2498.34 1720.96 L2498.34 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2498.34,1720.96 2498.34,1720.96 2498.62,1720.96 2498.34,1720.96 "/>
<path clip-path="url(#clip322)" d="M2498.62 1720.96 L2498.62 1720.96 L2498.9 1720.96 L2498.9 1720.96 L2498.62 1720.96 L2498.62 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2498.62,1720.96 2498.62,1720.96 2498.9,1720.96 2498.62,1720.96 "/>
<path clip-path="url(#clip322)" d="M2498.9 1720.96 L2498.9 1720.96 L2499.19 1720.96 L2499.19 1720.96 L2498.9 1720.96 L2498.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2498.9,1720.96 2498.9,1720.96 2499.19,1720.96 2498.9,1720.96 "/>
<path clip-path="url(#clip322)" d="M2499.19 1720.96 L2499.19 1720.96 L2499.47 1720.96 L2499.47 1720.96 L2499.19 1720.96 L2499.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2499.19,1720.96 2499.19,1720.96 2499.47,1720.96 2499.19,1720.96 "/>
<path clip-path="url(#clip322)" d="M2499.47 1720.96 L2499.47 1720.96 L2499.75 1720.96 L2499.75 1720.96 L2499.47 1720.96 L2499.47 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2499.47,1720.96 2499.47,1720.96 2499.75,1720.96 2499.47,1720.96 "/>
<path clip-path="url(#clip322)" d="M2499.75 1720.96 L2499.75 1720.96 L2500.03 1720.96 L2500.03 1720.96 L2499.75 1720.96 L2499.75 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2499.75,1720.96 2499.75,1720.96 2500.03,1720.96 2499.75,1720.96 "/>
<path clip-path="url(#clip322)" d="M2500.03 1720.96 L2500.03 1720.96 L2500.31 1720.96 L2500.31 1720.96 L2500.03 1720.96 L2500.03 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2500.03,1720.96 2500.03,1720.96 2500.31,1720.96 2500.03,1720.96 "/>
<path clip-path="url(#clip322)" d="M2500.31 1720.96 L2500.31 1720.96 L2500.59 1720.96 L2500.59 1720.96 L2500.31 1720.96 L2500.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2500.31,1720.96 2500.31,1720.96 2500.59,1720.96 2500.31,1720.96 "/>
<path clip-path="url(#clip322)" d="M2500.59 1720.96 L2500.59 1720.96 L2500.88 1720.96 L2500.88 1720.96 L2500.59 1720.96 L2500.59 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2500.59,1720.96 2500.59,1720.96 2500.88,1720.96 2500.59,1720.96 "/>
<path clip-path="url(#clip322)" d="M2500.88 1720.96 L2500.88 1720.96 L2501.16 1720.96 L2501.16 1720.96 L2500.88 1720.96 L2500.88 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2500.88,1720.96 2500.88,1720.96 2501.16,1720.96 2500.88,1720.96 "/>
<path clip-path="url(#clip322)" d="M2501.16 1720.96 L2501.16 1720.96 L2501.44 1720.96 L2501.44 1720.96 L2501.16 1720.96 L2501.16 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2501.16,1720.96 2501.16,1720.96 2501.44,1720.96 2501.16,1720.96 "/>
<path clip-path="url(#clip322)" d="M2501.44 1720.96 L2501.44 1720.96 L2501.72 1720.96 L2501.72 1720.96 L2501.44 1720.96 L2501.44 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2501.44,1720.96 2501.44,1720.96 2501.72,1720.96 2501.44,1720.96 "/>
<path clip-path="url(#clip322)" d="M2501.72 1720.96 L2501.72 1720.96 L2502 1720.96 L2502 1720.96 L2501.72 1720.96 L2501.72 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2501.72,1720.96 2501.72,1720.96 2502,1720.96 2501.72,1720.96 "/>
<path clip-path="url(#clip322)" d="M2502 1720.96 L2502 1720.96 L2502.28 1720.96 L2502.28 1720.96 L2502 1720.96 L2502 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2502,1720.96 2502,1720.96 2502.28,1720.96 2502,1720.96 "/>
<path clip-path="url(#clip322)" d="M2502.28 1720.96 L2502.28 1720.96 L2502.57 1720.96 L2502.57 1720.96 L2502.28 1720.96 L2502.28 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2502.28,1720.96 2502.28,1720.96 2502.57,1720.96 2502.28,1720.96 "/>
<path clip-path="url(#clip322)" d="M2502.57 1720.96 L2502.57 1720.96 L2502.85 1720.96 L2502.85 1720.96 L2502.57 1720.96 L2502.57 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2502.57,1720.96 2502.57,1720.96 2502.85,1720.96 2502.57,1720.96 "/>
<path clip-path="url(#clip322)" d="M2502.85 1720.96 L2502.85 1720.96 L2503.13 1720.96 L2503.13 1720.96 L2502.85 1720.96 L2502.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2502.85,1720.96 2502.85,1720.96 2503.13,1720.96 2502.85,1720.96 "/>
<path clip-path="url(#clip322)" d="M2503.13 1720.96 L2503.13 1720.96 L2503.41 1720.96 L2503.41 1720.96 L2503.13 1720.96 L2503.13 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2503.13,1720.96 2503.13,1720.96 2503.41,1720.96 2503.13,1720.96 "/>
<path clip-path="url(#clip322)" d="M2503.41 1720.96 L2503.41 1720.96 L2503.69 1720.96 L2503.69 1720.96 L2503.41 1720.96 L2503.41 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2503.41,1720.96 2503.41,1720.96 2503.69,1720.96 2503.41,1720.96 "/>
<path clip-path="url(#clip322)" d="M2503.69 1720.96 L2503.69 1720.96 L2503.97 1720.96 L2503.97 1720.96 L2503.69 1720.96 L2503.69 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2503.69,1720.96 2503.69,1720.96 2503.97,1720.96 2503.69,1720.96 "/>
<path clip-path="url(#clip322)" d="M2503.97 1720.96 L2503.97 1720.96 L2504.26 1720.96 L2504.26 1720.96 L2503.97 1720.96 L2503.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2503.97,1720.96 2503.97,1720.96 2504.26,1720.96 2503.97,1720.96 "/>
<path clip-path="url(#clip322)" d="M2504.26 1720.96 L2504.26 1720.96 L2504.54 1720.96 L2504.54 1720.96 L2504.26 1720.96 L2504.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2504.26,1720.96 2504.26,1720.96 2504.54,1720.96 2504.26,1720.96 "/>
<path clip-path="url(#clip322)" d="M2504.54 1720.96 L2504.54 1720.96 L2504.82 1720.96 L2504.82 1720.96 L2504.54 1720.96 L2504.54 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2504.54,1720.96 2504.54,1720.96 2504.82,1720.96 2504.54,1720.96 "/>
<path clip-path="url(#clip322)" d="M2504.82 1720.96 L2504.82 1720.96 L2505.1 1720.96 L2505.1 1720.96 L2504.82 1720.96 L2504.82 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2504.82,1720.96 2504.82,1720.96 2505.1,1720.96 2504.82,1720.96 "/>
<path clip-path="url(#clip322)" d="M2505.1 1720.96 L2505.1 1720.96 L2505.38 1720.96 L2505.38 1720.96 L2505.1 1720.96 L2505.1 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2505.1,1720.96 2505.1,1720.96 2505.38,1720.96 2505.1,1720.96 "/>
<path clip-path="url(#clip322)" d="M2505.38 1720.96 L2505.38 1720.96 L2505.67 1720.96 L2505.67 1720.96 L2505.38 1720.96 L2505.38 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2505.38,1720.96 2505.38,1720.96 2505.67,1720.96 2505.38,1720.96 "/>
<path clip-path="url(#clip322)" d="M2505.67 1720.96 L2505.67 1720.96 L2505.95 1720.96 L2505.95 1720.96 L2505.67 1720.96 L2505.67 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2505.67,1720.96 2505.67,1720.96 2505.95,1720.96 2505.67,1720.96 "/>
<path clip-path="url(#clip322)" d="M2505.95 1720.96 L2505.95 1720.96 L2506.23 1720.96 L2506.23 1720.96 L2505.95 1720.96 L2505.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2505.95,1720.96 2505.95,1720.96 2506.23,1720.96 2505.95,1720.96 "/>
<path clip-path="url(#clip322)" d="M2506.23 1720.96 L2506.23 1720.96 L2506.51 1720.96 L2506.51 1720.96 L2506.23 1720.96 L2506.23 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2506.23,1720.96 2506.23,1720.96 2506.51,1720.96 2506.23,1720.96 "/>
<path clip-path="url(#clip322)" d="M2506.51 1720.96 L2506.51 1720.96 L2506.79 1720.96 L2506.79 1720.96 L2506.51 1720.96 L2506.51 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2506.51,1720.96 2506.51,1720.96 2506.79,1720.96 2506.51,1720.96 "/>
<path clip-path="url(#clip322)" d="M2506.79 1720.96 L2506.79 1720.96 L2507.07 1720.96 L2507.07 1720.96 L2506.79 1720.96 L2506.79 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2506.79,1720.96 2506.79,1720.96 2507.07,1720.96 2506.79,1720.96 "/>
<path clip-path="url(#clip322)" d="M2507.07 1720.96 L2507.07 1720.96 L2507.36 1720.96 L2507.36 1720.96 L2507.07 1720.96 L2507.07 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2507.07,1720.96 2507.07,1720.96 2507.36,1720.96 2507.07,1720.96 "/>
<path clip-path="url(#clip322)" d="M2507.36 1720.96 L2507.36 1720.96 L2507.64 1720.96 L2507.64 1720.96 L2507.36 1720.96 L2507.36 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2507.36,1720.96 2507.36,1720.96 2507.64,1720.96 2507.36,1720.96 "/>
<path clip-path="url(#clip322)" d="M2507.64 1720.96 L2507.64 1720.96 L2507.92 1720.96 L2507.92 1720.96 L2507.64 1720.96 L2507.64 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2507.64,1720.96 2507.64,1720.96 2507.92,1720.96 2507.64,1720.96 "/>
<path clip-path="url(#clip322)" d="M2507.92 1720.96 L2507.92 1720.96 L2508.2 1720.96 L2508.2 1720.96 L2507.92 1720.96 L2507.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2507.92,1720.96 2507.92,1720.96 2508.2,1720.96 2507.92,1720.96 "/>
<path clip-path="url(#clip322)" d="M2508.2 1720.96 L2508.2 1720.96 L2508.48 1720.96 L2508.48 1720.96 L2508.2 1720.96 L2508.2 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2508.2,1720.96 2508.2,1720.96 2508.48,1720.96 2508.2,1720.96 "/>
<path clip-path="url(#clip322)" d="M2508.48 1720.96 L2508.48 1720.96 L2508.76 1720.96 L2508.76 1720.96 L2508.48 1720.96 L2508.48 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2508.48,1720.96 2508.48,1720.96 2508.76,1720.96 2508.48,1720.96 "/>
<path clip-path="url(#clip322)" d="M2508.76 1720.96 L2508.76 1720.96 L2509.05 1720.96 L2509.05 1720.96 L2508.76 1720.96 L2508.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2508.76,1720.96 2508.76,1720.96 2509.05,1720.96 2508.76,1720.96 "/>
<path clip-path="url(#clip322)" d="M2509.05 1720.96 L2509.05 1720.96 L2509.33 1720.96 L2509.33 1720.96 L2509.05 1720.96 L2509.05 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2509.05,1720.96 2509.05,1720.96 2509.33,1720.96 2509.05,1720.96 "/>
<path clip-path="url(#clip322)" d="M2509.33 1720.96 L2509.33 1720.96 L2509.61 1720.96 L2509.61 1720.96 L2509.33 1720.96 L2509.33 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2509.33,1720.96 2509.33,1720.96 2509.61,1720.96 2509.33,1720.96 "/>
<path clip-path="url(#clip322)" d="M2509.61 1720.96 L2509.61 1720.96 L2509.89 1720.96 L2509.89 1720.96 L2509.61 1720.96 L2509.61 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2509.61,1720.96 2509.61,1720.96 2509.89,1720.96 2509.61,1720.96 "/>
<path clip-path="url(#clip322)" d="M2509.89 1720.96 L2509.89 1720.96 L2510.17 1720.96 L2510.17 1720.96 L2509.89 1720.96 L2509.89 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2509.89,1720.96 2509.89,1720.96 2510.17,1720.96 2509.89,1720.96 "/>
<path clip-path="url(#clip322)" d="M2510.17 1720.76 L2510.17 1720.96 L2510.45 1720.96 L2510.45 1720.76 L2510.17 1720.76 L2510.17 1720.76  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip322)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2510.17,1720.76 2510.17,1720.96 2510.45,1720.96 2510.45,1720.76 2510.17,1720.76 "/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="402.161" cy="47.2441" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="402.443" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="402.725" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="403.006" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="403.288" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="403.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="403.851" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="404.133" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="404.415" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="404.697" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="404.978" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="405.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="405.542" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="405.824" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="406.105" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="406.387" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="406.669" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="406.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="407.232" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="407.514" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="407.796" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="408.077" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="408.359" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="408.641" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="408.923" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="409.204" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="409.486" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="409.768" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="410.049" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="410.331" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="410.613" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="410.895" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="411.176" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="411.458" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="411.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="412.022" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="412.303" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="412.585" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="412.867" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="413.148" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="413.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="413.712" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="413.994" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="414.275" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="414.557" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="414.839" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="415.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="415.402" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="415.684" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="415.966" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="416.247" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="416.529" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="416.811" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="417.093" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="417.374" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="417.656" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="417.938" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="418.219" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="418.501" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="418.783" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="419.065" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="419.346" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="419.628" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="419.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="420.192" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="420.473" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="420.755" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="421.037" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="421.318" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="421.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="421.882" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="422.164" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="422.445" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="422.727" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="423.009" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="423.291" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="423.572" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="423.854" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="424.136" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="424.417" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="424.699" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="424.981" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="425.263" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="425.544" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="425.826" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="426.108" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="426.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="426.671" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="426.953" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="427.235" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="427.516" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="427.798" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="428.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="428.362" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="428.643" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="428.925" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="429.207" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="429.489" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="429.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="430.052" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="430.334" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="430.615" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="430.897" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="431.179" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="431.461" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="431.742" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="432.024" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="432.306" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="432.587" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="432.869" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="433.151" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="433.433" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="433.714" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="433.996" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="434.278" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="434.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="434.841" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="435.123" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="435.405" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="435.686" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="435.968" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="436.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="436.532" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="436.813" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="437.095" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="437.377" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="437.659" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="437.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="438.222" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="438.504" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="438.785" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="439.067" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="439.349" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="439.631" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="439.912" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="440.194" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="440.476" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="440.758" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="441.039" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="441.321" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="441.603" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="441.884" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="442.166" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="442.448" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="442.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="443.011" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="443.293" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="443.575" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="443.857" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="444.138" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="444.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="444.702" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="444.983" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="445.265" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="445.547" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="445.829" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="446.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="446.392" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="446.674" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="446.955" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="447.237" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="447.519" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="447.801" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="448.082" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="448.364" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="448.646" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="448.928" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="449.209" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="449.491" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="449.773" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="450.054" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="450.336" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="450.618" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="450.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="451.181" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="451.463" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="451.745" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="452.027" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="452.308" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="452.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="452.872" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="453.153" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="453.435" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="453.717" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="453.999" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="454.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="454.562" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="454.844" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="455.126" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="455.407" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="455.689" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="455.971" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="456.252" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="456.534" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="456.816" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="457.098" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="457.379" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="457.661" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="457.943" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="458.225" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="458.506" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="458.788" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="459.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="459.351" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="459.633" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="459.915" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="460.197" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="460.478" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="460.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="461.042" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="461.323" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="461.605" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="461.887" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="462.169" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="462.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="462.732" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="463.014" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="463.296" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="463.577" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="463.859" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="464.141" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="464.422" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="464.704" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="464.986" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="465.268" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="465.549" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="465.831" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="466.113" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="466.395" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="466.676" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="466.958" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="467.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="467.521" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="467.803" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="468.085" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="468.367" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="468.648" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="468.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="469.212" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="469.494" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="469.775" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="470.057" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="470.339" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="470.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="470.902" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="471.184" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="471.466" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="471.747" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="472.029" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="472.311" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="472.593" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="472.874" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="473.156" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="473.438" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="473.719" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="474.001" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="474.283" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="474.565" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="474.846" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="475.128" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="475.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="475.692" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="475.973" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="476.255" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="476.537" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="476.818" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="477.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="477.382" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="477.664" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="477.945" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="478.227" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="478.509" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="478.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="479.072" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="479.354" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="479.636" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="479.917" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="480.199" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="480.481" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="480.763" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="481.044" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="481.326" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="481.608" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="481.889" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="482.171" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="482.453" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="482.735" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="483.016" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="483.298" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="483.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="483.862" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="484.143" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="484.425" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="484.707" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="484.988" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="485.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="485.552" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="485.834" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="486.115" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="486.397" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="486.679" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="486.961" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="487.242" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="487.524" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="487.806" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="488.087" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="488.369" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="488.651" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="488.933" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="489.214" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="489.496" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="489.778" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="490.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="490.341" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="490.623" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="490.905" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="491.186" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="491.468" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="491.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="492.032" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="492.313" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="492.595" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="492.877" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="493.158" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="493.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="493.722" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="494.004" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="494.285" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="494.567" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="494.849" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="495.131" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="495.412" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="495.694" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="495.976" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="496.257" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="496.539" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="496.821" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="497.103" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="497.384" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="497.666" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="497.948" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="498.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="498.511" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="498.793" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="499.075" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="499.356" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="499.638" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="499.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="500.202" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="500.483" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="500.765" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="501.047" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="501.329" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="501.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="501.892" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="502.174" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="502.455" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="502.737" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="503.019" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="503.301" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="503.582" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="503.864" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="504.146" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="504.428" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="504.709" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="504.991" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="505.273" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="505.554" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="505.836" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="506.118" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="506.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="506.681" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="506.963" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="507.245" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="507.526" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="507.808" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="508.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="508.372" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="508.653" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="508.935" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="509.217" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="509.499" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="509.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="510.062" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="510.344" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="510.625" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="510.907" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="511.189" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="511.471" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="511.752" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="512.034" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="512.316" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="512.598" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="512.879" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="513.161" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="513.443" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="513.724" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="514.006" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="514.288" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="514.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="514.851" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="515.133" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="515.415" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="515.697" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="515.978" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="516.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="516.542" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="516.823" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="517.105" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="517.387" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="517.669" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="517.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="518.232" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="518.514" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="518.796" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="519.077" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="519.359" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="519.641" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="519.922" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="520.204" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="520.486" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="520.768" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="521.049" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="521.331" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="521.613" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="521.895" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="522.176" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="522.458" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="522.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="523.021" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="523.303" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="523.585" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="523.867" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="524.148" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="524.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="524.712" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="524.993" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="525.275" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="525.557" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="525.839" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="526.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="526.402" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="526.684" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="526.966" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="527.247" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="527.529" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="527.811" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="528.092" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="528.374" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="528.656" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="528.938" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="529.219" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="529.501" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="529.783" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="530.065" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="530.346" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="530.628" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="530.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="531.191" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="531.473" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="531.755" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="532.037" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="532.318" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="532.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="532.882" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="533.164" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="533.445" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="533.727" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="534.009" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="534.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="534.572" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="534.854" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="535.136" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="535.417" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="535.699" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="535.981" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="536.263" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="536.544" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="536.826" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="537.108" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="537.389" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="537.671" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="537.953" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="538.235" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="538.516" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="538.798" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="539.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="539.361" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="539.643" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="539.925" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="540.207" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="540.488" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="540.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="541.052" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="541.334" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="541.615" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="541.897" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="542.179" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="542.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="542.742" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="543.024" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="543.306" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="543.587" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="543.869" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="544.151" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="544.433" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="544.714" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="544.996" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="545.278" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="545.559" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="545.841" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="546.123" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="546.405" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="546.686" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="546.968" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="547.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="547.532" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="547.813" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="548.095" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="548.377" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="548.658" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="548.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="549.222" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="549.504" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="549.785" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="550.067" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="550.349" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="550.631" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="550.912" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="551.194" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="551.476" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="551.757" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="552.039" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="552.321" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="552.603" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="552.884" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="553.166" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="553.448" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="553.729" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="554.011" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="554.293" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="554.575" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="554.856" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="555.138" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="555.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="555.702" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="555.983" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="556.265" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="556.547" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="556.828" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="557.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="557.392" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="557.674" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="557.955" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="558.237" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="558.519" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="558.801" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="559.082" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="559.364" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="559.646" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="559.927" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="560.209" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="560.491" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="560.773" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="561.054" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="561.336" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="561.618" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="561.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="562.181" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="562.463" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="562.745" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="563.026" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="563.308" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="563.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="563.872" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="564.153" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="564.435" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="564.717" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="564.999" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="565.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="565.562" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="565.844" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="566.125" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="566.407" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="566.689" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="566.971" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="567.252" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="567.534" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="567.816" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="568.097" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="568.379" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="568.661" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="568.943" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="569.224" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="569.506" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="569.788" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="570.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="570.351" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="570.633" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="570.915" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="571.196" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="571.478" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="571.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="572.042" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="572.323" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="572.605" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="572.887" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="573.169" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="573.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="573.732" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="574.014" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="574.295" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="574.577" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="574.859" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="575.141" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="575.422" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="575.704" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="575.986" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="576.268" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="576.549" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="576.831" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="577.113" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="577.394" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="577.676" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="577.958" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="578.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="578.521" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="578.803" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="579.085" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="579.367" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="579.648" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="579.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="580.212" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="580.493" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="580.775" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="581.057" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="581.339" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="581.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="581.902" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="582.184" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="582.466" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="582.747" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="583.029" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="583.311" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="583.592" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="583.874" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="584.156" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="584.438" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="584.719" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="585.001" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="585.283" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="585.564" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="585.846" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="586.128" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="586.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="586.691" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="586.973" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="587.255" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="587.537" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="587.818" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="588.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="588.382" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="588.663" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="588.945" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="589.227" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="589.509" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="589.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="590.072" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="590.354" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="590.636" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="590.917" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="591.199" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="591.481" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="591.762" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="592.044" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="592.326" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="592.608" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="592.889" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="593.171" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="593.453" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="593.735" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="594.016" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="594.298" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="594.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="594.861" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="595.143" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="595.425" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="595.707" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="595.988" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="596.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="596.552" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="596.834" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="597.115" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="597.397" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="597.679" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="597.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="598.242" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="598.524" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="598.806" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="599.087" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="599.369" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="599.651" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="599.932" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="600.214" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="600.496" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="600.778" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="601.059" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="601.341" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="601.623" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="601.905" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="602.186" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="602.468" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="602.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="603.031" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="603.313" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="603.595" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="603.877" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="604.158" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="604.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="604.722" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="605.004" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="605.285" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="605.567" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="605.849" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="606.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="606.412" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="606.694" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="606.976" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="607.257" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="607.539" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="607.821" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="608.103" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="608.384" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="608.666" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="608.948" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="609.229" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="609.511" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="609.793" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="610.075" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="610.356" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="610.638" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="610.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="611.202" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="611.483" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="611.765" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="612.047" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="612.328" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="612.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="612.892" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="613.174" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="613.455" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="613.737" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="614.019" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="614.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="614.582" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="614.864" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="615.146" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="615.427" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="615.709" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="615.991" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="616.273" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="616.554" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="616.836" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="617.118" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="617.399" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="617.681" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="617.963" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="618.245" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="618.526" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="618.808" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="619.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="619.372" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="619.653" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="619.935" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="620.217" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="620.498" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="620.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="621.062" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="621.344" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="621.625" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="621.907" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="622.189" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="622.471" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="622.752" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="623.034" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="623.316" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="623.597" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="623.879" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="624.161" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="624.443" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="624.724" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="625.006" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="625.288" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="625.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="625.851" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="626.133" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="626.415" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="626.696" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="626.978" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="627.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="627.542" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="627.823" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="628.105" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="628.387" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="628.669" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="628.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="629.232" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="629.514" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="629.795" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="630.077" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="630.359" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="630.641" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="630.922" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="631.204" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="631.486" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="631.767" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="632.049" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="632.331" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="632.613" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="632.894" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="633.176" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="633.458" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="633.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="634.021" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="634.303" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="634.585" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="634.866" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="635.148" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="635.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="635.712" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="635.993" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="636.275" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="636.557" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="636.839" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="637.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="637.402" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="637.684" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="637.965" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="638.247" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="638.529" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="638.811" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="639.092" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="639.374" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="639.656" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="639.938" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="640.219" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="640.501" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="640.783" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="641.064" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="641.346" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="641.628" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="641.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="642.191" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="642.473" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="642.755" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="643.037" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="643.318" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="643.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="643.882" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="644.163" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="644.445" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="644.727" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="645.009" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="645.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="645.572" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="645.854" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="646.135" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="646.417" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="646.699" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="646.981" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="647.262" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="647.544" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="647.826" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="648.108" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="648.389" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="648.671" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="648.953" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="649.234" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="649.516" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="649.798" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="650.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="650.361" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="650.643" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="650.925" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="651.207" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="651.488" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="651.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="652.052" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="652.333" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="652.615" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="652.897" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="653.179" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="653.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="653.742" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="654.024" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="654.306" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="654.587" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="654.869" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="655.151" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="655.432" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="655.714" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="655.996" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="656.278" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="656.559" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="656.841" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="657.123" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="657.405" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="657.686" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="657.968" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="658.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="658.531" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="658.813" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="659.095" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="659.377" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="659.658" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="659.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="660.222" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="660.503" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="660.785" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="661.067" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="661.349" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="661.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="661.912" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="662.194" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="662.476" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="662.757" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="663.039" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="663.321" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="663.602" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="663.884" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="664.166" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="664.448" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="664.729" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="665.011" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="665.293" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="665.575" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="665.856" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="666.138" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="666.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="666.701" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="666.983" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="667.265" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="667.547" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="667.828" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="668.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="668.392" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="668.674" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="668.955" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="669.237" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="669.519" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="669.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="670.082" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="670.364" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="670.646" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="670.927" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="671.209" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="671.491" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="671.773" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="672.054" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="672.336" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="672.618" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="672.899" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="673.181" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="673.463" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="673.745" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="674.026" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="674.308" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="674.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="674.872" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="675.153" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="675.435" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="675.717" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="675.998" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="676.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="676.562" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="676.844" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="677.125" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="677.407" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="677.689" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="677.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="678.252" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="678.534" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="678.816" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="679.097" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="679.379" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="679.661" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="679.943" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="680.224" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="680.506" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="680.788" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="681.069" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="681.351" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="681.633" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="681.915" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="682.196" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="682.478" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="682.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="683.042" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="683.323" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="683.605" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="683.887" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="684.168" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="684.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="684.732" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="685.014" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="685.295" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="685.577" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="685.859" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="686.141" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="686.422" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="686.704" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="686.986" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="687.267" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="687.549" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="687.831" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="688.113" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="688.394" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="688.676" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="688.958" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="689.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="689.521" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="689.803" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="690.085" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="690.366" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="690.648" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="690.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="691.212" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="691.493" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="691.775" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="692.057" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="692.338" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="692.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="692.902" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="693.184" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="693.465" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="693.747" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="694.029" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="694.311" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="694.592" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="694.874" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="695.156" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="695.437" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="695.719" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="696.001" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="696.283" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="696.564" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="696.846" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="697.128" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="697.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="697.691" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="697.973" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="698.255" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="698.536" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="698.818" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="699.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="699.382" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="699.663" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="699.945" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="700.227" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="700.509" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="700.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="701.072" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="701.354" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="701.635" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="701.917" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="702.199" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="702.481" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="702.762" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="703.044" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="703.326" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="703.608" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="703.889" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="704.171" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="704.453" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="704.734" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="705.016" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="705.298" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="705.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="705.861" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="706.143" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="706.425" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="706.706" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="706.988" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="707.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="707.552" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="707.833" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="708.115" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="708.397" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="708.679" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="708.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="709.242" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="709.524" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="709.805" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="710.087" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="710.369" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="710.651" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="710.932" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="711.214" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="711.496" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="711.778" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="712.059" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="712.341" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="712.623" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="712.904" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="713.186" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="713.468" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="713.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="714.031" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="714.313" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="714.595" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="714.877" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="715.158" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="715.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="715.722" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="716.003" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="716.285" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="716.567" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="716.849" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="717.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="717.412" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="717.694" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="717.976" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="718.257" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="718.539" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="718.821" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="719.102" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="719.384" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="719.666" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="719.948" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="720.229" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="720.511" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="720.793" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="721.075" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="721.356" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="721.638" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="721.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="722.201" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="722.483" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="722.765" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="723.047" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="723.328" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="723.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="723.892" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="724.173" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="724.455" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="724.737" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="725.019" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="725.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="725.582" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="725.864" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="726.146" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="726.427" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="726.709" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="726.991" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="727.272" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="727.554" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="727.836" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="728.118" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="728.399" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="728.681" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="728.963" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="729.245" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="729.526" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="729.808" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="730.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="730.371" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="730.653" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="730.935" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="731.217" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="731.498" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="731.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="732.062" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="732.344" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="732.625" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="732.907" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="733.189" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="733.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="733.752" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="734.034" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="734.316" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="734.597" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="734.879" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="735.161" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="735.443" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="735.724" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="736.006" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="736.288" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="736.569" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="736.851" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="737.133" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="737.415" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="737.696" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="737.978" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="738.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="738.541" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="738.823" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="739.105" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="739.387" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="739.668" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="739.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="740.232" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="740.514" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="740.795" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="741.077" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="741.359" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="741.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="741.922" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="742.204" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="742.486" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="742.767" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="743.049" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="743.331" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="743.613" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="743.894" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="744.176" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="744.458" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="744.739" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="745.021" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="745.303" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="745.585" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="745.866" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="746.148" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="746.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="746.712" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="746.993" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="747.275" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="747.557" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="747.838" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="748.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="748.402" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="748.684" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="748.965" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="749.247" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="749.529" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="749.811" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="750.092" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="750.374" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="750.656" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="750.937" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="751.219" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="751.501" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="751.783" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="752.064" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="752.346" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="752.628" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="752.909" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="753.191" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="753.473" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="753.755" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="754.036" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="754.318" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="754.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="754.882" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="755.163" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="755.445" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="755.727" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="756.008" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="756.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="756.572" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="756.854" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="757.135" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="757.417" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="757.699" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="757.981" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="758.262" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="758.544" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="758.826" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="759.107" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="759.389" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="759.671" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="759.953" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="760.234" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="760.516" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="760.798" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="761.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="761.361" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="761.643" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="761.925" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="762.206" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="762.488" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="762.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="763.052" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="763.333" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="763.615" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="763.897" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="764.179" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="764.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="764.742" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="765.024" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="765.305" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="765.587" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="765.869" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="766.151" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="766.432" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="766.714" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="766.996" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="767.277" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="767.559" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="767.841" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="768.123" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="768.404" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="768.686" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="768.968" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="769.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="769.531" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="769.813" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="770.095" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="770.376" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="770.658" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="770.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="771.222" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="771.503" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="771.785" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="772.067" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="772.349" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="772.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="772.912" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="773.194" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="773.475" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="773.757" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="774.039" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="774.321" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="774.602" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="774.884" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="775.166" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="775.448" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="775.729" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="776.011" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="776.293" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="776.574" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="776.856" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="777.138" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="777.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="777.701" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="777.983" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="778.265" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="778.547" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="778.828" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="779.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="779.392" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="779.673" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="779.955" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="780.237" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="780.519" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="780.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="781.082" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="781.364" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="781.646" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="781.927" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="782.209" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="782.491" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="782.772" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="783.054" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="783.336" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="783.618" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="783.899" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="784.181" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="784.463" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="784.744" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="785.026" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="785.308" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="785.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="785.871" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="786.153" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="786.435" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="786.717" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="786.998" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="787.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="787.562" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="787.843" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="788.125" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="788.407" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="788.689" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="788.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="789.252" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="789.534" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="789.816" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="790.097" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="790.379" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="790.661" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="790.942" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="791.224" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="791.506" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="791.788" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="792.069" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="792.351" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="792.633" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="792.915" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="793.196" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="793.478" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="793.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="794.041" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="794.323" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="794.605" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="794.887" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="795.168" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="795.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="795.732" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="796.014" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="796.295" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="796.577" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="796.859" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="797.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="797.422" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="797.704" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="797.986" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="798.267" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="798.549" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="798.831" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="799.112" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="799.394" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="799.676" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="799.958" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="800.239" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="800.521" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="800.803" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="801.085" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="801.366" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="801.648" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="801.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="802.211" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="802.493" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="802.775" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="803.057" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="803.338" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="803.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="803.902" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="804.184" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="804.465" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="804.747" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="805.029" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="805.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="805.592" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="805.874" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="806.156" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="806.437" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="806.719" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="807.001" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="807.283" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="807.564" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="807.846" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="808.128" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="808.409" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="808.691" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="808.973" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="809.255" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="809.536" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="809.818" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="810.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="810.382" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="810.663" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="810.945" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="811.227" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="811.508" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="811.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="812.072" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="812.354" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="812.635" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="812.917" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="813.199" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="813.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="813.762" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="814.044" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="814.326" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="814.607" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="814.889" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="815.171" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="815.453" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="815.734" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="816.016" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="816.298" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="816.579" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="816.861" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="817.143" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="817.425" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="817.706" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="817.988" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="818.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="818.552" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="818.833" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="819.115" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="819.397" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="819.678" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="819.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="820.242" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="820.524" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="820.805" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="821.087" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="821.369" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="821.651" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="821.932" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="822.214" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="822.496" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="822.777" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="823.059" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="823.341" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="823.623" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="823.904" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="824.186" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="824.468" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="824.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="825.031" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="825.313" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="825.595" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="825.876" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="826.158" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="826.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="826.722" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="827.003" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="827.285" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="827.567" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="827.849" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="828.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="828.412" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="828.694" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="828.975" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="829.257" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="829.539" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="829.821" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="830.102" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="830.384" cy="1719.58" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="830.666" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="830.947" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="831.229" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="831.511" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="831.793" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="832.074" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="832.356" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="832.638" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="832.92" cy="1719.58" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="833.201" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="833.483" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="833.765" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="834.046" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="834.328" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="834.61" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="834.892" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="835.173" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="835.455" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="835.737" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="836.019" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="836.3" cy="1719.19" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="836.582" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="836.864" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="837.145" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="837.427" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="837.709" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="837.991" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="838.272" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="838.554" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="838.836" cy="1719.19" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="839.118" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="839.399" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="839.681" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="839.963" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="840.244" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="840.526" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="840.808" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="841.09" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="841.371" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="841.653" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="841.935" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="842.217" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="842.498" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="842.78" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="843.062" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="843.343" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="843.625" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="843.907" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="844.189" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="844.47" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="844.752" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="845.034" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="845.315" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="845.597" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="845.879" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="846.161" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="846.442" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="846.724" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="847.006" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="847.288" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="847.569" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="847.851" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="848.133" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="848.414" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="848.696" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="848.978" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="849.26" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="849.541" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="849.823" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="850.105" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="850.387" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="850.668" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="850.95" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="851.232" cy="1719.58" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="851.513" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="851.795" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="852.077" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="852.359" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="852.64" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="852.922" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="853.204" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="853.486" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="853.767" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="854.049" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="854.331" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="854.612" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="854.894" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="855.176" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="855.458" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="855.739" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="856.021" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="856.303" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="856.585" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="856.866" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="857.148" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="857.43" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="857.711" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="857.993" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="858.275" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="858.557" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="858.838" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="859.12" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="859.402" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="859.683" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="859.965" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="860.247" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="860.529" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="860.81" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="861.092" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="861.374" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="861.656" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="861.937" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="862.219" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="862.501" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="862.782" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="863.064" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="863.346" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="863.628" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="863.909" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="864.191" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="864.473" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="864.755" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="865.036" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="865.318" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="865.6" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="865.881" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="866.163" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="866.445" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="866.727" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="867.008" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="867.29" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="867.572" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="867.854" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="868.135" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="868.417" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="868.699" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="868.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="869.262" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="869.544" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="869.826" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="870.107" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="870.389" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="870.671" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="870.953" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="871.234" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="871.516" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="871.798" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="872.079" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="872.361" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="872.643" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="872.925" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="873.206" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="873.488" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="873.77" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="874.052" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="874.333" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="874.615" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="874.897" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="875.178" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="875.46" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="875.742" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="876.024" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="876.305" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="876.587" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="876.869" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="877.15" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="877.432" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="877.714" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="877.996" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="878.277" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="878.559" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="878.841" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="879.123" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="879.404" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="879.686" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="879.968" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="880.249" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="880.531" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="880.813" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="881.095" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="881.376" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="881.658" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="881.94" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="882.222" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="882.503" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="882.785" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="883.067" cy="1719.78" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="883.348" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="883.63" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="883.912" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="884.194" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="884.475" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="884.757" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="885.039" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="885.321" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="885.602" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="885.884" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="886.166" cy="1719.38" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="886.447" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="886.729" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="887.011" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="887.293" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="887.574" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="887.856" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="888.138" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="888.42" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="888.701" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="888.983" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="889.265" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="889.546" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="889.828" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="890.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="890.392" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="890.673" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="890.955" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="891.237" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="891.518" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="891.8" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="892.082" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="892.364" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="892.645" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="892.927" cy="1719.58" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="893.209" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="893.491" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="893.772" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="894.054" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="894.336" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="894.617" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="894.899" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="895.181" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="895.463" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="895.744" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="896.026" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="896.308" cy="1719.58" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="896.59" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="896.871" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="897.153" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="897.435" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="897.716" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="897.998" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="898.28" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="898.562" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="898.843" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="899.125" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="899.407" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="899.689" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="899.97" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="900.252" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="900.534" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="900.815" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="901.097" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="901.379" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="901.661" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="901.942" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="902.224" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="902.506" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="902.788" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="903.069" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="903.351" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="903.633" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="903.914" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="904.196" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="904.478" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="904.76" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="905.041" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="905.323" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="905.605" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="905.886" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="906.168" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="906.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="906.732" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="907.013" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="907.295" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="907.577" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="907.859" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="908.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="908.422" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="908.704" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="908.985" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="909.267" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="909.549" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="909.831" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="910.112" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="910.394" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="910.676" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="910.958" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="911.239" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="911.521" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="911.803" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="912.084" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="912.366" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="912.648" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="912.93" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="913.211" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="913.493" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="913.775" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="914.057" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="914.338" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="914.62" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="914.902" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="915.183" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="915.465" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="915.747" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="916.029" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="916.31" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="916.592" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="916.874" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="917.156" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="917.437" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="917.719" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="918.001" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="918.282" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="918.564" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="918.846" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="919.128" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="919.409" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="919.691" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="919.973" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="920.255" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="920.536" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="920.818" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="921.1" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="921.381" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="921.663" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="921.945" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="922.227" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="922.508" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="922.79" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="923.072" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="923.353" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="923.635" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="923.917" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="924.199" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="924.48" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="924.762" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="925.044" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="925.326" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="925.607" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="925.889" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="926.171" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="926.452" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="926.734" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="927.016" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="927.298" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="927.579" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="927.861" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="928.143" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="928.425" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="928.706" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="928.988" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="929.27" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="929.551" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="929.833" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="930.115" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="930.397" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="930.678" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="930.96" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="931.242" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="931.524" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="931.805" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="932.087" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="932.369" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="932.65" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="932.932" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="933.214" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="933.496" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="933.777" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="934.059" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="934.341" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="934.623" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="934.904" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="935.186" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="935.468" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="935.749" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="936.031" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="936.313" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="936.595" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="936.876" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="937.158" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="937.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="937.721" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="938.003" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="938.285" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="938.567" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="938.848" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="939.13" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="939.412" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="939.694" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="939.975" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="940.257" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="940.539" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="940.82" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="941.102" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="941.384" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="941.666" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="941.947" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="942.229" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="942.511" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="942.793" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="943.074" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="943.356" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="943.638" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="943.919" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="944.201" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="944.483" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="944.765" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="945.046" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="945.328" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="945.61" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="945.892" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="946.173" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="946.455" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="946.737" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="947.018" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="947.3" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="947.582" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="947.864" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="948.145" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="948.427" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="948.709" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="948.991" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="949.272" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="949.554" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="949.836" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="950.117" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="950.399" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="950.681" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="950.963" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="951.244" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="951.526" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="951.808" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="952.089" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="952.371" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="952.653" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="952.935" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="953.216" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="953.498" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="953.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="954.062" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="954.343" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="954.625" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="954.907" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="955.188" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="955.47" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="955.752" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="956.034" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="956.315" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="956.597" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="956.879" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="957.161" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="957.442" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="957.724" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="958.006" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="958.287" cy="1720.17" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="958.569" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="958.851" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="959.133" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="959.414" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="959.696" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="959.978" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="960.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="960.541" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="960.823" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="961.105" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="961.386" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="961.668" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="961.95" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="962.232" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="962.513" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="962.795" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="963.077" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="963.359" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="963.64" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="963.922" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="964.204" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="964.485" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="964.767" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="965.049" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="965.331" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="965.612" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="965.894" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="966.176" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="966.457" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="966.739" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="967.021" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="967.303" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="967.584" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="967.866" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="968.148" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="968.43" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="968.711" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="968.993" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="969.275" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="969.556" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="969.838" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="970.12" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="970.402" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="970.683" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="970.965" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="971.247" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="971.529" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="971.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="972.092" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="972.374" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="972.655" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="972.937" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="973.219" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="973.501" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="973.782" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="974.064" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="974.346" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="974.628" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="974.909" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="975.191" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="975.473" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="975.754" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="976.036" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="976.318" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="976.6" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="976.881" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="977.163" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="977.445" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="977.727" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="978.008" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="978.29" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="978.572" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="978.853" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="979.135" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="979.417" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="979.699" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="979.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="980.262" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="980.544" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="980.826" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="981.107" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="981.389" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="981.671" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="981.952" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="982.234" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="982.516" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="982.798" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="983.079" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="983.361" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="983.643" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="983.924" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="984.206" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="984.488" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="984.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="985.051" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="985.333" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="985.615" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="985.897" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="986.178" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="986.46" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="986.742" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="987.023" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="987.305" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="987.587" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="987.869" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="988.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="988.432" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="988.714" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="988.996" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="989.277" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="989.559" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="989.841" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="990.122" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="990.404" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="990.686" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="990.968" cy="1719.97" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="991.249" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="991.531" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="991.813" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="992.095" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="992.376" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="992.658" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="992.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="993.221" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="993.503" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="993.785" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="994.067" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="994.348" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="994.63" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="994.912" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="995.194" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="995.475" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="995.757" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="996.039" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="996.32" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="996.602" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="996.884" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="997.166" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="997.447" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="997.729" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="998.011" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="998.292" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="998.574" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="998.856" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="999.138" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="999.419" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="999.701" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="999.983" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1000.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1000.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1000.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1001.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1001.39" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1001.67" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1001.95" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1002.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1002.52" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1002.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1003.08" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1003.36" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1003.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1003.93" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1004.21" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1004.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1004.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1005.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1005.34" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1005.62" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1005.9" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1006.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1006.46" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1006.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1007.03" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1007.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1007.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1007.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1008.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1008.43" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1008.72" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1009" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1009.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1009.56" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1009.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1010.12" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1010.41" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1010.69" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1010.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1011.25" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1011.53" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1011.82" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1012.1" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1012.38" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1012.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1012.94" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1013.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1013.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1013.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1014.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1014.35" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1014.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1014.91" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1015.2" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1015.48" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1015.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1016.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1016.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1016.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1016.89" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1017.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1017.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1017.73" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1018.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1018.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1018.58" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1018.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1019.14" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1019.42" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1019.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1019.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1020.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1020.55" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1020.83" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1021.11" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1021.39" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1021.68" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1021.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1022.24" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1022.52" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1022.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1023.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1023.37" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1023.65" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1023.93" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1024.21" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1024.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1024.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1025.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1025.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1025.62" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1025.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1026.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1026.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1026.75" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1027.03" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1027.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1027.59" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1027.87" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1028.16" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1028.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1028.72" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1029" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1029.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1029.56" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1029.85" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1030.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1030.41" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1030.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1030.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1031.25" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1031.54" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1031.82" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1032.1" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1032.38" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1032.66" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1032.94" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1033.23" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1033.51" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1033.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1034.07" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1034.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1034.64" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1034.92" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1035.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1035.48" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1035.76" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1036.04" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1036.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1036.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1036.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1037.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1037.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1037.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1038.02" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1038.3" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1038.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1038.86" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1039.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1039.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1039.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1039.99" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1040.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1040.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1040.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1041.11" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1041.4" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1041.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1041.96" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1042.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1042.52" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1042.81" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1043.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1043.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1043.65" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1043.93" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1044.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1044.5" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1044.78" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1045.06" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1045.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1045.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1045.9" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1046.19" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1046.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1046.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1047.03" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1047.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1047.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1047.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1048.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1048.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1048.72" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1049" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1049.28" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1049.57" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1049.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1050.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1050.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1050.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1050.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1051.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1051.54" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1051.82" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1052.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1052.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1052.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1052.95" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1053.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1053.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1053.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1054.07" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1054.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1054.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1054.92" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1055.2" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1055.48" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1055.76" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1056.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1056.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1056.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1056.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1057.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1057.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1057.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1058.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1058.3" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1058.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1058.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1059.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1059.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1059.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1059.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1060.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1060.55" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1060.84" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1061.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1061.4" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1061.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1061.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1062.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1062.53" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1062.81" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1063.09" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1063.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1063.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1063.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1064.22" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1064.5" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1064.78" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1065.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1065.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1065.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1065.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1066.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1066.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1066.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1067.03" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1067.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1067.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1067.88" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1068.16" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1068.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1068.72" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1069.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1069.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1069.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1069.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1070.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1070.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1070.7" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1070.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1071.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1071.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1071.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1072.1" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1072.39" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1072.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1072.95" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1073.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1073.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1073.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1074.08" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1074.36" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1074.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1074.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1075.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1075.49" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1075.77" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1076.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1076.33" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1076.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1076.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1077.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1077.46" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1077.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1078.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1078.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1078.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1078.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1079.15" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1079.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1079.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1079.99" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1080.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1080.56" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1080.84" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1081.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1081.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1081.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1081.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1082.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1082.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1082.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1083.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1083.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1083.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1083.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1084.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1084.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1084.78" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1085.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1085.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1085.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1085.91" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1086.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1086.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1086.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1087.04" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1087.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1087.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1087.88" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1088.16" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1088.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1088.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1089.01" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1089.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1089.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1089.85" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1090.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1090.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1090.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1090.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1091.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1091.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1091.83" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1092.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1092.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1092.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1092.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1093.23" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1093.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1093.8" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1094.08" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1094.36" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1094.64" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1094.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1095.21" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1095.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1095.77" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1096.05" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1096.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1096.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1096.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1097.18" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1097.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1097.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1098.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1098.31" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1098.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1098.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1099.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1099.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1099.71" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1100" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1100.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1100.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1100.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1101.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1101.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1101.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1101.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1102.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1102.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1102.81" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1103.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1103.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1103.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1103.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1104.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1104.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1104.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1105.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1105.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1105.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1105.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1106.19" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1106.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1106.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1107.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1107.32" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1107.6" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1107.88" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1108.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1108.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1108.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1109.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1109.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1109.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1109.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1110.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1110.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1110.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1110.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1111.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1111.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1111.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1112.11" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1112.39" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1112.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1112.95" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1113.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1113.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1113.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1114.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1114.36" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1114.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1114.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1115.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1115.49" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1115.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1116.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1116.34" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1116.62" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1116.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1117.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1117.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1117.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1118.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1118.31" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1118.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1118.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1119.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1119.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1119.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1120" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1120.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1120.56" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1120.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1121.12" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1121.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1121.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1121.97" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1122.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1122.53" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1122.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1123.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1123.38" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1123.66" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1123.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1124.22" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1124.51" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1124.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1125.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1125.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1125.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1125.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1126.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1126.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1126.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1127.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1127.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1127.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1127.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1128.17" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1128.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1128.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1129.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1129.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1129.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1129.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1130.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1130.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1130.7" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1130.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1131.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1131.55" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1131.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1132.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1132.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1132.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1132.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1133.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1133.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1133.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1134.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1134.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1134.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1134.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1135.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1135.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1135.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1136.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1136.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1136.62" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1136.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1137.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1137.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1137.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1138.03" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1138.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1138.59" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1138.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1139.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1139.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1139.72" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1140" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1140.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1140.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1140.85" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1141.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1141.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1141.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1141.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1142.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1142.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1142.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1143.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1143.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1143.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1143.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1144.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1144.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1144.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1145.07" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1145.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1145.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1145.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1146.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1146.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1146.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1147.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1147.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1147.61" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1147.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1148.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1148.45" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1148.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1149.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1149.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1149.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1149.86" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1150.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1150.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1150.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1150.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1151.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1151.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1151.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1152.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1152.4" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1152.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1152.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1153.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1153.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1153.81" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1154.09" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1154.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1154.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1154.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1155.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1155.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1155.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1156.06" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1156.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1156.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1156.9" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1157.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1157.47" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1157.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1158.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1158.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1158.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1158.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1159.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1159.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1159.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1160" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1160.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1160.57" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1160.85" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1161.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1161.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1161.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1161.98" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1162.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1162.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1162.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1163.1" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1163.38" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1163.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1163.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1164.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1164.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1164.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1165.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1165.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1165.64" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1165.92" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1166.2" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1166.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1166.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1167.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1167.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1167.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1167.89" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1168.17" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1168.45" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1168.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1169.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1169.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1169.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1169.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1170.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1170.43" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1170.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1170.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1171.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1171.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1171.84" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1172.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1172.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1172.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1172.96" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1173.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1173.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1173.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1174.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1174.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1174.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1174.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1175.22" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1175.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1175.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1176.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1176.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1176.62" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1176.91" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1177.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1177.47" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1177.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1178.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1178.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1178.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1178.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1179.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1179.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1179.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1180.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1180.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1180.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1180.85" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1181.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1181.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1181.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1181.98" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1182.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1182.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1182.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1183.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1183.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1183.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1183.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1184.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1184.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1184.79" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1185.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1185.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1185.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1185.92" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1186.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1186.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1186.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1187.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1187.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1187.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1187.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1188.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1188.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1188.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1189.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1189.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1189.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1189.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1190.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1190.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1190.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1190.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1191.27" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1191.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1191.84" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1192.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1192.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1192.68" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1192.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1193.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1193.53" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1193.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1194.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1194.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1194.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1194.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1195.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1195.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1195.78" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1196.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1196.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1196.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1196.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1197.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1197.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1197.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1198.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1198.32" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1198.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1198.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1199.16" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1199.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1199.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1200.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1200.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1200.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1200.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1201.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1201.42" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1201.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1201.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1202.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1202.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1202.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1203.11" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1203.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1203.67" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1203.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1204.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1204.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1204.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1205.08" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1205.36" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1205.64" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1205.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1206.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1206.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1206.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1207.05" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1207.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1207.61" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1207.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1208.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1208.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1208.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1209.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1209.3" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1209.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1209.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1210.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1210.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1210.71" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1211" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1211.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1211.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1211.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1212.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1212.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1212.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1212.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1213.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1213.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1213.81" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1214.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1214.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1214.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1214.94" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1215.22" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1215.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1215.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1216.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1216.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1216.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1216.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1217.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1217.48" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1217.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1218.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1218.32" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1218.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1218.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1219.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1219.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1219.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1220.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1220.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1220.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1220.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1221.14" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1221.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1221.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1221.98" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1222.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1222.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1222.83" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1223.11" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1223.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1223.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1223.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1224.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1224.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1224.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1225.08" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1225.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1225.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1225.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1226.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1226.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1226.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1227.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1227.34" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1227.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1227.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1228.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1228.46" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1228.74" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1229.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1229.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1229.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1229.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1230.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1230.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1230.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1231" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1231.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1231.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1231.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1232.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1232.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1232.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1232.97" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1233.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1233.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1233.82" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1234.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1234.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1234.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1234.94" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1235.22" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1235.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1235.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1236.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1236.35" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1236.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1236.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1237.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1237.48" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1237.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1238.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1238.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1238.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1238.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1239.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1239.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1239.73" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1240.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1240.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1240.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1240.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1241.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1241.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1241.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1241.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1242.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1242.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1242.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1243.11" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1243.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1243.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1243.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1244.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1244.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1244.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1245.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1245.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1245.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1245.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1246.21" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1246.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1246.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1247.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1247.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1247.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1247.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1248.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1248.46" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1248.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1249.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1249.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1249.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1249.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1250.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1250.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1250.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1251" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1251.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1251.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1251.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1252.13" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1252.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1252.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1252.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1253.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1253.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1253.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1254.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1254.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1254.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1254.94" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1255.23" cy="1720.37" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1255.51" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1255.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1256.07" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1256.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1256.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1256.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1257.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1257.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1257.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1258.04" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1258.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1258.61" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1258.89" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1259.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1259.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1259.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1260.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1260.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1260.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1260.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1261.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1261.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1261.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1261.99" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1262.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1262.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1262.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1263.11" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1263.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1263.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1263.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1264.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1264.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1264.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1265.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1265.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1265.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1265.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1266.21" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1266.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1266.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1267.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1267.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1267.62" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1267.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1268.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1268.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1268.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1269.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1269.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1269.59" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1269.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1270.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1270.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1270.72" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1271" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1271.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1271.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1271.85" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1272.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1272.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1272.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1272.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1273.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1273.54" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1273.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1274.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1274.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1274.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1274.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1275.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1275.51" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1275.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1276.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1276.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1276.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1276.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1277.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1277.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1277.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1278.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1278.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1278.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1278.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1279.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1279.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1279.74" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1280.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1280.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1280.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1280.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1281.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1281.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1281.71" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1281.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1282.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1282.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1282.84" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1283.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1283.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1283.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1283.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1284.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1284.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1284.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1285.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1285.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1285.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1285.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1286.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1286.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1286.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1287.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1287.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1287.62" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1287.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1288.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1288.47" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1288.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1289.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1289.32" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1289.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1289.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1290.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1290.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1290.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1291.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1291.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1291.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1291.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1292.13" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1292.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1292.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1292.98" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1293.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1293.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1293.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1294.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1294.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1294.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1294.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1295.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1295.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1295.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1296.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1296.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1296.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1296.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1297.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1297.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1297.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1298.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1298.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1298.61" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1298.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1299.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1299.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1299.74" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1300.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1300.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1300.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1300.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1301.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1301.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1301.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1301.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1302.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1302.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1302.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1303.12" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1303.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1303.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1303.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1304.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1304.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1304.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1305.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1305.37" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1305.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1305.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1306.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1306.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1306.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1307.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1307.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1307.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1307.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1308.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1308.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1308.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1309.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1309.32" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1309.6" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1309.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1310.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1310.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1310.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1311.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1311.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1311.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1311.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1312.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1312.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1312.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1312.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1313.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1313.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1313.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1314.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1314.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1314.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1314.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1315.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1315.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1315.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1316.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1316.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1316.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1316.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1317.21" cy="1720.56" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1317.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1317.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1318.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1318.33" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1318.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1318.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1319.18" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1319.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1319.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1320.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1320.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1320.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1320.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1321.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1321.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1321.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1322" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1322.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1322.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1322.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1323.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1323.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1323.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1323.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1324.25" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1324.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1324.81" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1325.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1325.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1325.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1325.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1326.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1326.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1326.78" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1327.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1327.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1327.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1327.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1328.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1328.47" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1328.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1329.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1329.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1329.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1329.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1330.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1330.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1330.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1331.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1331.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1331.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1331.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1332.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1332.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1332.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1332.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1333.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1333.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1333.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1334.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1334.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1334.67" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1334.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1335.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1335.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1335.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1336.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1336.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1336.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1336.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1337.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1337.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1337.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1338.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1338.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1338.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1338.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1339.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1339.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1339.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1340.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1340.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1340.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1340.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1341.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1341.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1341.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1342" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1342.28" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1342.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1342.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1343.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1343.41" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1343.69" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1343.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1344.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1344.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1344.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1345.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1345.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1345.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1345.94" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1346.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1346.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1346.79" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1347.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1347.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1347.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1347.91" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1348.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1348.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1348.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1349.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1349.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1349.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1349.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1350.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1350.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1350.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1351.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1351.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1351.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1351.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1352.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1352.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1352.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1352.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1353.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1353.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1353.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1354.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1354.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1354.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1354.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1355.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1355.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1355.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1356.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1356.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1356.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1356.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1357.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1357.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1357.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1358.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1358.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1358.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1358.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1359.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1359.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1359.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1360.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1360.31" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1360.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1360.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1361.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1361.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1361.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1362" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1362.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1362.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1362.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1363.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1363.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1363.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1363.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1364.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1364.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1364.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1365.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1365.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1365.66" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1365.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1366.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1366.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1366.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1367.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1367.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1367.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1367.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1368.2" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1368.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1368.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1369.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1369.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1369.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1369.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1370.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1370.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1370.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1371.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1371.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1371.58" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1371.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1372.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1372.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1372.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1372.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1373.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1373.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1373.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1374.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1374.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1374.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1374.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1375.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1375.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1375.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1376.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1376.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1376.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1376.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1377.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1377.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1377.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1378.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1378.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1378.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1378.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1379.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1379.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1379.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1380.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1380.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1380.59" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1380.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1381.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1381.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1381.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1382" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1382.28" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1382.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1382.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1383.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1383.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1383.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1383.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1384.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1384.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1384.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1385.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1385.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1385.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1385.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1386.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1386.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1386.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1387.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1387.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1387.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1387.92" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1388.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1388.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1388.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1389.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1389.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1389.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1389.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1390.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1390.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1390.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1391.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1391.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1391.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1391.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1392.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1392.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1392.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1392.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1393.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1393.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1393.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1394.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1394.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1394.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1394.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1395.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1395.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1395.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1396.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1396.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1396.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1396.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1397.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1397.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1397.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1398.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1398.34" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1398.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1398.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1399.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1399.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1399.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1400.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1400.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1400.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1400.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1401.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1401.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1401.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1402.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1402.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1402.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1402.85" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1403.13" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1403.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1403.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1403.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1404.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1404.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1404.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1405.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1405.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1405.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1405.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1406.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1406.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1406.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1407.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1407.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1407.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1407.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1408.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1408.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1408.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1409.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1409.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1409.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1409.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1410.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1410.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1410.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1411.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1411.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1411.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1411.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1412.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1412.43" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1412.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1412.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1413.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1413.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1413.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1414.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1414.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1414.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1414.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1415.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1415.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1415.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1416.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1416.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1416.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1416.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1417.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1417.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1417.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1418.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1418.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1418.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1418.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1419.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1419.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1419.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1420.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1420.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1420.6" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1420.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1421.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1421.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1421.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1422.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1422.29" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1422.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1422.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1423.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1423.42" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1423.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1423.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1424.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1424.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1424.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1425.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1425.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1425.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1425.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1426.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1426.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1426.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1427.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1427.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1427.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1427.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1428.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1428.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1428.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1429.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1429.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1429.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1429.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1430.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1430.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1430.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1431.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1431.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1431.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1431.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1432.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1432.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1432.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1433" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1433.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1433.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1433.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1434.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1434.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1434.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1434.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1435.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1435.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1435.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1436.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1436.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1436.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1436.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1437.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1437.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1437.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1438.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1438.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1438.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1438.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1439.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1439.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1439.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1440.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1440.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1440.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1440.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1441.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1441.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1441.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1442.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1442.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1442.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1442.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1443.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1443.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1443.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1443.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1444.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1444.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1444.83" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1445.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1445.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1445.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1445.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1446.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1446.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1446.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1447.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1447.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1447.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1447.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1448.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1448.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1448.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1449.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1449.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1449.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1449.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1450.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1450.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1450.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1451.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1451.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1451.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1451.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1452.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1452.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1452.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1453" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1453.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1453.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1453.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1454.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1454.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1454.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1454.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1455.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1455.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1455.81" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1456.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1456.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1456.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1456.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1457.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1457.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1457.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1458.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1458.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1458.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1458.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1459.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1459.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1459.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1460.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1460.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1460.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1460.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1461.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1461.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1461.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1462.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1462.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1462.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1462.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1463.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1463.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1463.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1463.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1464.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1464.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1464.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1465.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1465.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1465.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1465.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1466.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1466.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1466.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1467.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1467.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1467.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1467.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1468.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1468.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1468.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1469.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1469.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1469.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1469.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1470.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1470.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1470.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1471.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1471.31" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1471.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1471.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1472.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1472.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1472.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1473" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1473.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1473.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1473.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1474.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1474.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1474.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1474.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1475.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1475.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1475.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1476.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1476.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1476.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1476.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1477.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1477.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1477.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1478.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1478.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1478.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1478.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1479.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1479.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1479.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1480.04" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1480.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1480.61" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1480.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1481.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1481.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1481.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1482.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1482.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1482.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1482.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1483.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1483.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1483.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1483.99" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1484.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1484.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1484.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1485.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1485.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1485.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1485.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1486.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1486.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1486.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1487.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1487.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1487.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1487.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1488.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1488.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1488.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1489.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1489.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1489.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1489.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1490.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1490.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1490.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1491.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1491.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1491.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1491.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1492.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1492.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1492.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1493" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1493.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1493.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1493.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1494.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1494.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1494.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1494.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1495.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1495.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1495.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1496.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1496.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1496.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1496.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1497.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1497.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1497.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1498.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1498.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1498.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1498.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1499.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1499.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1499.76" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1500.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1500.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1500.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1500.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1501.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1501.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1501.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1502.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1502.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1502.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1502.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1503.14" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1503.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1503.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1503.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1504.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1504.55" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1504.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1505.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1505.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1505.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1505.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1506.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1506.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1506.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1507.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1507.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1507.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1507.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1508.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1508.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1508.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1509.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1509.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1509.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1509.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1510.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1510.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1510.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1511.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1511.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1511.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1511.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1512.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1512.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1512.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1513.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1513.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1513.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1513.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1514.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1514.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1514.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1514.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1515.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1515.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1515.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1516.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1516.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1516.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1516.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1517.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1517.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1517.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1518.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1518.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1518.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1518.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1519.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1519.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1519.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1520.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1520.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1520.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1520.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1521.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1521.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1521.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1522.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1522.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1522.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1522.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1523.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1523.43" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1523.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1523.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1524.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1524.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1524.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1525.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1525.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1525.68" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1525.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1526.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1526.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1526.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1527.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1527.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1527.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1527.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1528.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1528.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1528.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1529.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1529.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1529.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1529.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1530.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1530.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1530.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1531.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1531.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1531.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1531.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1532.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1532.44" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1532.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1533.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1533.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1533.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1533.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1534.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1534.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1534.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1534.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1535.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1535.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1535.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1536.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1536.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1536.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1536.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1537.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1537.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1537.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1538.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1538.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1538.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1538.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1539.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1539.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1539.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1540.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1540.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1540.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1540.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1541.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1541.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1541.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1542.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1542.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1542.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1542.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1543.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1543.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1543.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1543.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1544.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1544.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1544.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1545.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1545.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1545.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1545.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1546.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1546.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1546.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1547.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1547.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1547.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1547.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1548.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1548.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1548.78" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1549.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1549.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1549.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1549.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1550.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1550.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1550.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1551.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1551.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1551.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1551.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1552.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1552.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1552.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1553.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1553.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1553.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1553.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1554.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1554.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1554.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1554.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1555.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1555.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1555.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1556.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1556.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1556.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1556.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1557.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1557.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1557.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1558.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1558.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1558.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1558.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1559.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1559.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1559.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1560.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1560.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1560.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1560.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1561.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1561.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1561.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1562.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1562.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1562.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1562.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1563.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1563.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1563.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1564" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1564.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1564.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1564.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1565.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1565.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1565.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1565.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1566.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1566.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1566.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1567.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1567.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1567.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1567.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1568.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1568.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1568.79" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1569.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1569.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1569.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1569.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1570.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1570.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1570.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1571.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1571.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1571.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1571.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1572.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1572.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1572.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1573.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1573.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1573.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1573.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1574.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1574.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1574.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1574.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1575.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1575.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1575.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1576.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1576.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1576.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1576.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1577.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1577.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1577.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1578.08" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1578.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1578.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1578.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1579.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1579.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1579.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1580.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1580.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1580.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1580.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1581.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1581.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1581.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1582.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1582.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1582.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1582.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1583.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1583.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1583.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1584" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1584.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1584.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1584.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1585.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1585.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1585.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1585.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1586.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1586.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1586.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1587.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1587.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1587.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1587.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1588.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1588.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1588.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1589.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1589.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1589.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1589.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1590.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1590.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1590.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1591.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1591.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1591.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1591.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1592.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1592.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1592.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1593.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1593.3" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1593.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1593.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1594.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1594.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1594.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1594.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1595.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1595.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1595.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1596.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1596.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1596.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1596.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1597.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1597.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1597.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1598.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1598.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1598.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1598.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1599.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1599.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1599.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1600.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1600.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1600.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1600.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1601.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1601.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1601.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1602.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1602.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1602.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1602.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1603.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1603.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1603.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1604" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1604.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1604.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1604.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1605.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1605.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1605.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1605.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1606.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1606.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1606.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1607.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1607.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1607.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1607.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1608.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1608.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1608.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1609.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1609.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1609.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1609.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1610.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1610.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1610.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1611.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1611.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1611.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1611.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1612.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1612.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1612.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1613.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1613.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1613.58" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1613.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1614.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1614.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1614.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1614.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1615.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1615.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1615.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1616.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1616.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1616.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1616.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1617.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1617.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1617.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1618.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1618.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1618.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1618.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1619.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1619.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1619.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1620.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1620.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1620.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1620.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1621.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1621.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1621.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1622.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1622.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1622.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1622.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1623.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1623.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1623.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1624.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1624.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1624.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1624.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1625.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1625.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1625.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1625.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1626.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1626.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1626.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1627.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1627.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1627.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1627.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1628.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1628.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1628.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1629.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1629.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1629.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1629.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1630.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1630.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1630.77" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1631.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1631.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1631.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1631.89" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1632.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1632.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1632.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1633.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1633.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1633.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1633.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1634.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1634.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1634.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1634.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1635.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1635.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1635.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1636.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1636.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1636.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1636.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1637.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1637.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1637.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1638.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1638.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1638.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1638.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1639.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1639.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1639.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1640.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1640.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1640.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1640.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1641.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1641.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1641.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1642.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1642.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1642.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1642.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1643.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1643.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1643.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1644.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1644.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1644.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1644.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1645.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1645.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1645.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1645.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1646.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1646.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1646.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1647.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1647.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1647.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1647.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1648.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1648.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1648.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1649.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1649.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1649.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1649.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1650.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1650.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1650.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1651.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1651.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1651.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1651.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1652.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1652.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1652.74" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1653.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1653.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1653.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1653.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1654.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1654.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1654.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1654.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1655.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1655.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1655.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1656.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1656.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1656.69" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1656.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1657.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1657.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1657.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1658.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1658.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1658.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1658.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1659.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1659.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1659.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1660.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1660.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1660.63" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1660.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1661.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1661.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1661.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1662.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1662.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1662.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1662.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1663.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1663.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1663.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1664.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1664.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1664.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1664.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1665.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1665.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1665.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1665.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1666.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1666.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1666.83" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1667.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1667.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1667.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1667.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1668.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1668.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1668.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1669.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1669.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1669.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1669.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1670.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1670.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1670.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1671.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1671.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1671.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1671.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1672.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1672.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1672.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1673.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1673.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1673.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1673.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1674.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1674.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1674.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1675" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1675.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1675.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1675.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1676.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1676.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1676.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1676.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1677.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1677.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1677.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1678.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1678.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1678.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1678.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1679.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1679.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1679.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1680.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1680.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1680.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1680.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1681.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1681.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1681.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1682.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1682.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1682.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1682.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1683.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1683.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1683.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1684.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1684.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1684.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1684.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1685.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1685.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1685.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1685.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1686.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1686.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1686.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1687.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1687.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1687.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1687.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1688.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1688.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1688.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1689.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1689.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1689.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1689.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1690.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1690.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1690.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1691.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1691.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1691.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1691.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1692.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1692.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1692.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1693.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1693.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1693.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1693.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1694.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1694.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1694.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1695" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1695.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1695.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1695.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1696.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1696.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1696.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1696.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1697.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1697.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1697.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1698.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1698.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1698.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1698.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1699.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1699.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1699.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1700.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1700.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1700.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1700.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1701.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1701.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1701.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1702.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1702.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1702.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1702.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1703.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1703.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1703.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1704.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1704.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1704.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1704.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1705.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1705.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1705.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1705.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1706.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1706.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1706.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1707.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1707.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1707.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1707.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1708.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1708.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1708.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1709.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1709.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1709.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1709.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1710.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1710.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1710.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1711.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1711.34" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1711.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1711.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1712.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1712.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1712.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1713.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1713.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1713.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1713.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1714.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1714.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1714.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1715" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1715.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1715.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1715.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1716.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1716.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1716.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1716.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1717.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1717.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1717.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1718.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1718.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1718.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1718.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1719.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1719.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1719.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1720.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1720.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1720.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1720.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1721.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1721.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1721.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1722.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1722.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1722.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1722.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1723.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1723.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1723.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1724.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1724.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1724.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1724.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1725.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1725.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1725.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1725.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1726.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1726.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1726.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1727.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1727.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1727.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1727.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1728.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1728.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1728.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1729.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1729.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1729.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1729.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1730.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1730.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1730.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1731.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1731.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1731.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1731.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1732.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1732.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1732.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1733.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1733.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1733.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1733.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1734.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1734.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1734.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1735" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1735.29" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1735.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1735.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1736.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1736.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1736.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1736.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1737.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1737.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1737.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1738.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1738.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1738.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1738.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1739.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1739.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1739.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1740.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1740.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1740.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1740.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1741.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1741.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1741.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1742.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1742.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1742.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1742.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1743.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1743.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1743.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1744.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1744.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1744.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1744.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1745.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1745.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1745.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1745.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1746.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1746.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1746.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1747.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1747.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1747.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1747.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1748.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1748.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1748.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1749.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1749.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1749.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1749.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1750.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1750.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1750.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1751.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1751.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1751.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1751.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1752.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1752.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1752.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1753.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1753.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1753.6" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1753.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1754.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1754.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1754.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1755.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1755.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1755.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1755.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1756.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1756.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1756.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1756.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1757.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1757.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1757.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1758.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1758.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1758.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1758.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1759.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1759.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1759.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1760.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1760.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1760.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1760.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1761.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1761.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1761.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1762.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1762.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1762.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1762.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1763.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1763.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1763.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1764.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1764.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1764.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1764.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1765.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1765.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1765.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1765.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1766.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1766.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1766.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1767.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1767.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1767.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1767.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1768.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1768.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1768.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1769.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1769.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1769.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1769.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1770.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1770.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1770.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1771.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1771.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1771.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1771.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1772.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1772.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1772.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1773.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1773.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1773.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1773.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1774.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1774.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1774.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1775.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1775.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1775.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1775.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1776.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1776.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1776.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1776.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1777.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1777.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1777.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1778.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1778.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1778.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1778.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1779.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1779.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1779.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1780.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1780.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1780.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1780.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1781.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1781.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1781.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1782.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1782.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1782.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1782.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1783.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1783.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1783.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1784.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1784.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1784.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1784.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1785.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1785.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1785.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1786" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1786.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1786.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1786.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1787.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1787.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1787.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1787.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1788.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1788.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1788.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1789.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1789.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1789.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1789.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1790.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1790.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1790.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1791.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1791.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1791.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1791.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1792.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1792.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1792.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1793.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1793.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1793.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1793.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1794.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1794.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1794.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1795.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1795.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1795.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1795.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1796.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1796.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1796.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1796.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1797.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1797.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1797.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1798.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1798.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1798.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1798.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1799.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1799.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1799.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1800.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1800.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1800.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1800.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1801.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1801.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1801.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1802.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1802.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1802.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1802.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1803.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1803.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1803.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1804.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1804.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1804.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1804.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1805.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1805.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1805.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1806" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1806.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1806.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1806.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1807.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1807.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1807.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1807.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1808.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1808.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1808.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1809.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1809.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1809.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1809.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1810.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1810.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1810.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1811.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1811.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1811.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1811.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1812.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1812.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1812.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1813.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1813.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1813.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1813.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1814.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1814.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1814.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1815.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1815.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1815.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1815.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1816.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1816.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1816.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1816.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1817.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1817.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1817.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1818.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1818.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1818.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1818.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1819.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1819.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1819.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1820.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1820.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1820.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1820.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1821.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1821.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1821.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1822.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1822.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1822.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1822.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1823.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1823.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1823.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1824.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1824.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1824.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1824.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1825.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1825.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1825.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1826" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1826.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1826.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1826.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1827.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1827.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1827.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1827.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1828.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1828.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1828.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1829.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1829.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1829.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1829.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1830.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1830.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1830.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1831.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1831.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1831.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1831.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1832.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1832.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1832.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1833.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1833.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1833.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1833.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1834.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1834.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1834.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1835.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1835.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1835.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1835.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1836.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1836.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1836.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1836.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1837.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1837.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1837.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1838.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1838.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1838.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1838.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1839.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1839.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1839.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1840.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1840.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1840.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1840.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1841.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1841.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1841.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1842.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1842.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1842.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1842.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1843.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1843.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1843.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1844.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1844.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1844.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1844.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1845.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1845.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1845.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1846" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1846.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1846.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1846.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1847.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1847.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1847.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1847.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1848.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1848.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1848.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1849.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1849.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1849.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1849.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1850.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1850.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1850.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1851.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1851.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1851.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1851.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1852.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1852.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1852.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1853.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1853.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1853.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1853.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1854.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1854.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1854.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1855.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1855.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1855.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1855.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1856.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1856.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1856.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1856.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1857.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1857.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1857.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1858.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1858.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1858.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1858.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1859.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1859.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1859.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1860.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1860.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1860.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1860.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1861.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1861.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1861.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1862.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1862.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1862.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1862.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1863.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1863.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1863.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1864.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1864.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1864.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1864.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1865.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1865.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1865.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1866.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1866.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1866.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1866.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1867.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1867.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1867.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1867.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1868.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1868.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1868.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1869.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1869.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1869.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1869.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1870.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1870.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1870.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1871.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1871.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1871.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1871.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1872.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1872.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1872.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1873.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1873.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1873.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1873.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1874.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1874.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1874.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1875.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1875.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1875.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1875.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1876.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1876.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1876.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1876.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1877.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1877.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1877.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1878.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1878.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1878.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1878.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1879.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1879.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1879.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1880.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1880.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1880.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1880.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1881.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1881.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1881.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1882.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1882.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1882.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1882.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1883.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1883.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1883.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1884.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1884.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1884.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1884.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1885.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1885.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1885.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1886.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1886.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1886.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1886.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1887.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1887.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1887.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1887.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1888.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1888.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1888.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1889.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1889.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1889.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1889.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1890.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1890.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1890.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1891.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1891.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1891.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1891.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1892.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1892.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1892.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1893.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1893.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1893.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1893.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1894.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1894.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1894.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1895.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1895.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1895.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1895.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1896.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1896.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1896.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1897" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1897.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1897.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1897.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1898.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1898.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1898.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1898.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1899.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1899.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1899.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1900.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1900.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1900.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1900.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1901.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1901.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1901.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1902.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1902.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1902.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1902.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1903.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1903.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1903.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1904.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1904.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1904.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1904.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1905.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1905.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1905.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1906.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1906.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1906.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1906.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1907.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1907.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1907.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1907.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1908.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1908.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1908.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1909.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1909.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1909.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1909.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1910.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1910.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1910.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1911.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1911.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1911.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1911.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1912.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1912.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1912.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1913.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1913.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1913.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1913.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1914.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1914.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1914.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1915.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1915.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1915.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1915.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1916.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1916.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1916.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1917" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1917.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1917.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1917.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1918.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1918.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1918.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1918.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1919.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1919.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1919.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1920.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1920.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1920.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1920.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1921.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1921.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1921.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1922.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1922.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1922.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1922.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1923.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1923.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1923.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1924.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1924.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1924.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1924.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1925.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1925.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1925.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1926.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1926.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1926.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1926.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1927.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1927.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1927.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1927.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1928.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1928.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1928.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1929.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1929.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1929.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1929.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1930.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1930.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1930.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1931.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1931.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1931.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1931.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1932.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1932.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1932.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1933.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1933.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1933.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1933.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1934.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1934.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1934.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1935.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1935.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1935.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1935.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1936.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1936.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1936.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1937" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1937.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1937.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1937.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1938.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1938.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1938.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1938.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1939.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1939.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1939.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1940.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1940.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1940.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1940.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1941.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1941.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1941.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1942.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1942.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1942.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1942.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1943.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1943.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1943.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1944.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1944.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1944.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1944.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1945.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1945.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1945.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1946.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1946.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1946.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1946.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1947.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1947.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1947.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1947.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1948.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1948.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1948.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1949.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1949.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1949.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1949.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1950.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1950.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1950.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1951.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1951.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1951.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1951.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1952.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1952.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1952.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1953.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1953.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1953.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1953.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1954.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1954.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1954.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1955.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1955.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1955.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1955.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1956.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1956.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1956.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1957" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1957.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1957.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1957.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1958.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1958.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1958.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1958.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1959.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1959.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1959.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1960.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1960.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1960.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1960.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1961.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1961.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1961.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1962.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1962.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1962.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1962.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1963.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1963.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1963.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1964.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1964.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1964.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1964.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1965.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1965.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1965.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1966.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1966.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1966.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1966.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1967.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1967.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1967.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1967.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1968.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1968.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1968.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1969.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1969.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1969.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1969.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1970.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1970.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1970.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1971.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1971.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1971.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1971.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1972.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1972.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1972.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1973.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1973.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1973.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1973.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1974.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1974.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1974.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1975.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1975.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1975.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1975.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1976.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1976.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1976.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1977.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1977.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1977.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1977.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1978.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1978.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1978.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1978.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1979.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1979.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1979.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1980.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1980.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1980.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1980.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1981.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1981.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1981.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1982.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1982.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1982.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1982.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1983.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1983.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1983.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1984.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1984.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1984.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1984.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1985.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1985.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1985.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1986.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1986.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1986.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1986.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1987.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1987.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1987.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1987.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1988.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1988.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1988.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1989.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1989.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1989.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1989.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1990.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1990.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1990.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1991.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1991.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1991.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1991.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1992.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1992.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1992.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1993.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1993.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1993.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1993.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1994.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1994.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1994.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1995.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1995.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1995.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1995.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1996.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1996.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1996.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1997.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1997.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1997.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1997.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1998.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1998.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1998.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1998.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1999.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1999.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1999.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2000.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2000.39" cy="1720.76" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2000.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2000.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2001.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2001.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2001.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2002.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2002.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2002.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2002.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2003.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2003.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2003.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2004.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2004.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2004.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2004.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2005.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2005.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2005.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2006.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2006.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2006.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2006.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2007.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2007.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2007.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2008" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2008.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2008.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2008.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2009.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2009.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2009.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2009.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2010.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2010.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2010.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2011.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2011.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2011.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2011.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2012.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2012.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2012.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2013.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2013.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2013.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2013.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2014.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2014.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2014.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2015.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2015.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2015.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2015.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2016.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2016.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2016.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2017.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2017.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2017.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2017.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2018.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2018.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2018.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2018.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2019.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2019.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2019.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2020.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2020.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2020.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2020.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2021.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2021.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2021.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2022.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2022.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2022.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2022.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2023.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2023.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2023.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2024.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2024.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2024.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2024.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2025.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2025.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2025.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2026.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2026.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2026.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2026.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2027.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2027.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2027.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2028" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2028.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2028.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2028.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2029.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2029.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2029.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2029.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2030.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2030.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2030.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2031.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2031.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2031.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2031.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2032.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2032.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2032.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2033.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2033.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2033.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2033.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2034.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2034.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2034.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2035.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2035.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2035.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2035.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2036.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2036.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2036.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2037.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2037.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2037.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2037.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2038.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2038.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2038.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2038.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2039.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2039.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2039.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2040.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2040.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2040.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2040.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2041.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2041.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2041.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2042.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2042.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2042.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2042.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2043.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2043.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2043.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2044.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2044.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2044.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2044.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2045.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2045.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2045.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2046.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2046.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2046.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2046.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2047.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2047.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2047.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2048" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2048.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2048.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2048.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2049.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2049.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2049.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2049.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2050.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2050.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2050.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2051.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2051.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2051.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2051.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2052.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2052.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2052.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2053.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2053.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2053.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2053.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2054.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2054.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2054.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2055.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2055.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2055.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2055.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2056.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2056.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2056.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2057.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2057.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2057.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2057.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2058.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2058.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2058.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2058.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2059.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2059.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2059.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2060.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2060.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2060.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2060.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2061.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2061.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2061.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2062.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2062.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2062.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2062.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2063.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2063.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2063.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2064.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2064.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2064.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2064.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2065.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2065.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2065.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2066.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2066.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2066.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2066.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2067.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2067.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2067.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2068" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2068.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2068.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2068.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2069.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2069.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2069.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2069.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2070.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2070.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2070.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2071.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2071.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2071.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2071.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2072.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2072.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2072.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2073.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2073.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2073.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2073.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2074.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2074.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2074.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2075.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2075.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2075.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2075.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2076.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2076.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2076.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2077.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2077.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2077.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2077.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2078.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2078.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2078.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2078.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2079.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2079.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2079.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2080.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2080.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2080.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2080.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2081.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2081.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2081.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2082.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2082.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2082.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2082.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2083.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2083.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2083.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2084.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2084.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2084.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2084.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2085.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2085.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2085.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2086.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2086.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2086.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2086.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2087.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2087.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2087.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2088.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2088.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2088.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2088.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2089.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2089.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2089.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2089.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2090.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2090.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2090.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2091.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2091.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2091.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2091.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2092.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2092.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2092.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2093.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2093.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2093.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2093.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2094.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2094.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2094.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2095.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2095.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2095.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2095.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2096.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2096.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2096.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2097.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2097.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2097.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2097.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2098.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2098.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2098.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2098.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2099.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2099.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2099.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2100.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2100.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2100.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2100.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2101.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2101.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2101.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2102.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2102.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2102.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2102.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2103.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2103.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2103.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2104.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2104.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2104.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2104.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2105.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2105.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2105.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2106.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2106.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2106.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2106.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2107.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2107.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2107.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2108.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2108.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2108.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2108.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2109.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2109.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2109.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2109.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2110.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2110.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2110.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2111.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2111.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2111.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2111.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2112.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2112.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2112.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2113.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2113.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2113.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2113.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2114.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2114.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2114.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2115.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2115.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2115.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2115.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2116.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2116.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2116.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2117.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2117.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2117.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2117.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2118.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2118.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2118.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2119" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2119.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2119.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2119.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2120.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2120.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2120.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2120.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2121.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2121.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2121.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2122.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2122.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2122.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2122.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2123.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2123.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2123.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2124.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2124.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2124.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2124.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2125.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2125.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2125.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2126.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2126.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2126.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2126.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2127.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2127.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2127.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2128.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2128.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2128.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2128.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2129.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2129.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2129.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2129.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2130.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2130.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2130.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2131.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2131.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2131.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2131.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2132.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2132.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2132.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2133.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2133.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2133.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2133.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2134.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2134.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2134.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2135.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2135.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2135.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2135.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2136.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2136.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2136.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2137.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2137.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2137.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2137.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2138.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2138.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2138.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2139" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2139.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2139.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2139.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2140.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2140.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2140.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2140.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2141.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2141.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2141.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2142.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2142.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2142.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2142.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2143.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2143.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2143.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2144.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2144.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2144.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2144.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2145.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2145.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2145.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2146.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2146.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2146.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2146.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2147.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2147.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2147.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2148.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2148.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2148.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2148.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2149.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2149.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2149.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2149.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2150.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2150.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2150.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2151.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2151.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2151.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2151.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2152.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2152.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2152.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2153.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2153.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2153.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2153.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2154.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2154.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2154.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2155.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2155.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2155.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2155.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2156.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2156.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2156.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2157.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2157.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2157.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2157.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2158.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2158.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2158.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2159" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2159.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2159.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2159.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2160.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2160.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2160.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2160.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2161.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2161.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2161.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2162.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2162.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2162.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2162.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2163.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2163.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2163.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2164.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2164.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2164.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2164.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2165.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2165.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2165.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2166.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2166.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2166.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2166.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2167.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2167.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2167.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2168.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2168.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2168.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2168.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2169.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2169.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2169.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2169.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2170.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2170.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2170.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2171.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2171.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2171.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2171.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2172.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2172.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2172.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2173.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2173.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2173.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2173.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2174.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2174.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2174.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2175.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2175.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2175.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2175.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2176.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2176.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2176.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2177.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2177.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2177.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2177.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2178.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2178.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2178.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2179" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2179.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2179.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2179.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2180.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2180.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2180.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2180.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2181.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2181.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2181.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2182.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2182.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2182.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2182.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2183.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2183.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2183.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2184.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2184.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2184.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2184.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2185.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2185.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2185.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2186.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2186.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2186.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2186.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2187.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2187.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2187.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2188.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2188.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2188.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2188.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2189.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2189.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2189.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2189.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2190.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2190.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2190.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2191.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2191.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2191.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2191.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2192.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2192.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2192.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2193.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2193.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2193.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2193.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2194.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2194.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2194.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2195.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2195.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2195.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2195.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2196.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2196.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2196.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2197.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2197.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2197.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2197.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2198.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2198.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2198.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2199.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2199.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2199.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2199.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2200.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2200.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2200.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2200.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2201.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2201.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2201.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2202.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2202.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2202.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2202.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2203.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2203.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2203.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2204.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2204.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2204.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2204.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2205.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2205.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2205.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2206.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2206.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2206.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2206.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2207.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2207.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2207.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2208.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2208.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2208.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2208.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2209.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2209.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2209.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2209.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2210.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2210.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2210.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2211.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2211.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2211.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2211.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2212.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2212.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2212.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2213.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2213.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2213.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2213.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2214.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2214.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2214.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2215.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2215.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2215.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2215.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2216.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2216.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2216.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2217.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2217.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2217.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2217.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2218.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2218.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2218.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2219.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2219.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2219.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2219.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2220.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2220.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2220.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2220.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2221.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2221.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2221.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2222.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2222.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2222.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2222.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2223.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2223.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2223.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2224.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2224.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2224.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2224.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2225.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2225.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2225.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2226.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2226.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2226.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2226.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2227.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2227.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2227.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2228.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2228.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2228.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2228.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2229.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2229.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2229.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2230" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2230.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2230.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2230.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2231.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2231.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2231.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2231.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2232.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2232.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2232.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2233.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2233.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2233.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2233.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2234.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2234.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2234.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2235.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2235.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2235.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2235.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2236.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2236.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2236.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2237.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2237.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2237.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2237.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2238.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2238.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2238.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2239.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2239.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2239.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2239.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2240.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2240.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2240.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2240.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2241.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2241.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2241.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2242.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2242.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2242.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2242.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2243.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2243.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2243.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2244.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2244.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2244.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2244.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2245.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2245.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2245.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2246.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2246.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2246.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2246.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2247.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2247.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2247.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2248.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2248.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2248.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2248.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2249.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2249.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2249.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2250" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2250.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2250.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2250.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2251.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2251.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2251.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2251.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2252.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2252.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2252.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2253.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2253.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2253.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2253.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2254.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2254.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2254.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2255.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2255.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2255.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2255.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2256.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2256.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2256.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2257.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2257.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2257.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2257.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2258.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2258.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2258.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2259.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2259.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2259.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2259.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2260.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2260.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2260.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2260.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2261.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2261.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2261.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2262.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2262.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2262.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2262.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2263.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2263.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2263.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2264.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2264.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2264.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2264.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2265.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2265.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2265.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2266.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2266.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2266.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2266.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2267.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2267.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2267.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2268.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2268.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2268.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2268.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2269.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2269.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2269.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2270" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2270.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2270.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2270.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2271.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2271.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2271.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2271.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2272.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2272.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2272.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2273.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2273.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2273.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2273.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2274.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2274.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2274.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2275.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2275.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2275.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2275.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2276.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2276.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2276.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2277.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2277.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2277.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2277.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2278.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2278.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2278.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2279.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2279.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2279.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2279.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2280.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2280.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2280.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2280.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2281.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2281.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2281.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2282.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2282.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2282.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2282.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2283.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2283.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2283.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2284.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2284.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2284.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2284.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2285.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2285.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2285.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2286.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2286.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2286.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2286.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2287.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2287.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2287.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2288.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2288.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2288.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2288.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2289.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2289.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2289.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2290" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2290.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2290.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2290.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2291.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2291.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2291.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2291.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2292.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2292.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2292.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2293.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2293.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2293.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2293.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2294.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2294.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2294.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2295.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2295.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2295.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2295.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2296.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2296.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2296.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2297.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2297.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2297.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2297.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2298.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2298.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2298.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2299.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2299.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2299.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2299.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2300.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2300.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2300.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2300.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2301.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2301.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2301.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2302.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2302.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2302.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2302.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2303.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2303.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2303.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2304.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2304.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2304.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2304.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2305.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2305.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2305.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2306.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2306.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2306.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2306.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2307.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2307.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2307.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2308.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2308.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2308.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2308.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2309.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2309.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2309.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2310.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2310.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2310.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2310.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2311.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2311.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2311.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2311.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2312.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2312.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2312.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2313.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2313.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2313.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2313.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2314.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2314.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2314.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2315.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2315.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2315.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2315.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2316.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2316.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2316.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2317.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2317.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2317.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2317.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2318.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2318.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2318.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2319.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2319.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2319.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2319.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2320.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2320.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2320.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2320.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2321.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2321.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2321.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2322.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2322.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2322.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2322.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2323.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2323.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2323.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2324.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2324.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2324.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2324.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2325.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2325.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2325.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2326.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2326.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2326.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2326.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2327.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2327.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2327.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2328.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2328.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2328.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2328.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2329.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2329.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2329.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2330.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2330.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2330.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2330.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2331.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2331.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2331.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2331.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2332.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2332.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2332.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2333.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2333.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2333.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2333.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2334.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2334.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2334.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2335.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2335.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2335.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2335.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2336.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2336.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2336.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2337.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2337.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2337.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2337.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2338.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2338.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2338.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2339.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2339.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2339.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2339.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2340.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2340.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2340.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2341" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2341.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2341.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2341.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2342.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2342.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2342.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2342.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2343.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2343.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2343.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2344.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2344.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2344.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2344.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2345.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2345.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2345.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2346.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2346.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2346.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2346.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2347.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2347.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2347.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2348.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2348.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2348.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2348.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2349.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2349.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2349.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2350.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2350.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2350.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2350.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2351.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2351.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2351.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2351.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2352.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2352.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2352.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2353.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2353.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2353.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2353.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2354.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2354.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2354.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2355.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2355.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2355.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2355.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2356.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2356.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2356.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2357.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2357.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2357.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2357.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2358.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2358.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2358.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2359.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2359.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2359.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2359.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2360.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2360.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2360.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2361" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2361.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2361.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2361.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2362.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2362.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2362.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2362.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2363.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2363.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2363.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2364.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2364.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2364.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2364.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2365.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2365.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2365.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2366.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2366.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2366.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2366.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2367.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2367.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2367.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2368.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2368.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2368.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2368.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2369.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2369.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2369.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2370.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2370.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2370.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2370.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2371.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2371.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2371.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2371.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2372.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2372.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2372.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2373.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2373.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2373.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2373.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2374.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2374.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2374.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2375.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2375.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2375.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2375.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2376.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2376.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2376.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2377.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2377.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2377.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2377.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2378.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2378.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2378.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2379.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2379.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2379.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2379.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2380.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2380.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2380.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2381" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2381.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2381.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2381.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2382.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2382.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2382.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2382.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2383.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2383.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2383.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2384.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2384.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2384.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2384.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2385.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2385.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2385.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2386.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2386.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2386.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2386.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2387.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2387.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2387.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2388.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2388.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2388.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2388.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2389.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2389.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2389.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2390.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2390.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2390.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2390.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2391.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2391.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2391.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2391.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2392.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2392.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2392.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2393.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2393.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2393.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2393.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2394.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2394.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2394.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2395.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2395.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2395.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2395.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2396.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2396.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2396.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2397.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2397.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2397.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2397.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2398.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2398.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2398.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2399.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2399.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2399.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2399.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2400.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2400.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2400.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2401" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2401.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2401.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2401.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2402.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2402.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2402.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2402.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2403.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2403.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2403.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2404.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2404.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2404.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2404.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2405.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2405.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2405.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2406.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2406.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2406.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2406.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2407.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2407.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2407.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2408.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2408.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2408.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2408.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2409.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2409.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2409.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2410.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2410.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2410.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2410.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2411.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2411.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2411.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2411.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2412.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2412.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2412.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2413.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2413.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2413.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2413.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2414.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2414.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2414.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2415.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2415.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2415.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2415.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2416.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2416.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2416.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2417.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2417.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2417.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2417.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2418.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2418.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2418.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2419.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2419.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2419.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2419.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2420.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2420.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2420.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2421.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2421.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2421.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2421.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2422.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2422.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2422.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2422.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2423.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2423.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2423.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2424.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2424.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2424.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2424.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2425.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2425.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2425.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2426.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2426.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2426.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2426.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2427.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2427.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2427.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2428.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2428.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2428.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2428.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2429.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2429.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2429.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2430.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2430.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2430.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2430.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2431.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2431.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2431.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2431.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2432.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2432.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2432.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2433.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2433.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2433.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2433.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2434.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2434.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2434.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2435.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2435.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2435.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2435.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2436.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2436.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2436.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2437.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2437.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2437.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2437.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2438.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2438.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2438.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2439.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2439.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2439.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2439.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2440.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2440.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2440.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2441.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2441.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2441.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2441.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2442.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2442.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2442.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2442.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2443.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2443.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2443.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2444.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2444.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2444.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2444.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2445.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2445.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2445.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2446.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2446.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2446.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2446.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2447.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2447.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2447.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2448.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2448.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2448.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2448.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2449.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2449.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2449.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2450.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2450.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2450.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2450.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2451.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2451.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2451.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2452" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2452.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2452.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2452.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2453.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2453.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2453.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2453.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2454.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2454.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2454.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2455.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2455.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2455.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2455.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2456.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2456.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2456.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2457.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2457.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2457.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2457.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2458.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2458.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2458.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2459.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2459.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2459.6" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2459.88" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2460.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2460.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2460.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2461.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2461.29" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2461.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2461.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2462.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2462.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2462.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2462.98" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2463.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2463.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2463.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2464.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2464.39" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2464.67" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2464.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2465.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2465.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2465.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2466.08" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2466.36" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2466.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2466.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2467.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2467.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2467.77" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2468.05" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2468.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2468.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2468.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2469.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2469.46" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2469.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2470.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2470.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2470.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2470.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2471.15" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2471.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2471.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2472" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2472.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2472.56" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2472.84" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2473.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2473.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2473.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2473.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2474.25" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2474.53" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2474.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2475.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2475.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2475.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2475.94" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2476.22" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2476.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2476.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2477.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2477.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2477.63" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2477.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2478.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2478.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2478.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2479.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2479.32" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2479.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2479.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2480.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2480.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2480.73" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2481.01" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2481.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2481.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2481.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2482.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2482.42" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2482.7" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2482.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2483.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2483.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2483.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2484.11" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2484.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2484.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2484.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2485.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2485.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2485.8" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2486.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2486.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2486.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2486.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2487.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2487.49" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2487.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2488.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2488.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2488.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2488.9" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2489.18" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2489.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2489.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2490.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2490.31" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2490.59" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2490.87" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2491.16" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2491.44" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2491.72" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2492" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2492.28" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2492.57" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2492.85" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2493.13" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2493.41" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2493.69" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2493.97" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2494.26" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2494.54" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2494.82" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2495.1" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2495.38" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2495.66" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2495.95" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2496.23" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2496.51" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2496.79" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2497.07" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2497.35" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2497.64" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2497.92" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2498.2" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2498.48" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2498.76" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2499.04" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2499.33" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2499.61" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2499.89" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2500.17" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2500.45" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2500.74" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2501.02" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2501.3" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2501.58" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2501.86" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2502.14" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2502.43" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2502.71" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2502.99" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2503.27" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2503.55" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2503.83" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2504.12" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2504.4" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2504.68" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2504.96" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2505.24" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2505.52" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2505.81" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2506.09" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2506.37" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2506.65" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2506.93" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2507.21" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2507.5" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2507.78" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2508.06" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2508.34" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2508.62" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2508.91" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2509.19" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2509.47" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2509.75" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2510.03" cy="1720.96" r="2"/>
<circle clip-path="url(#clip322)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2510.31" cy="1720.76" r="2"/>
<path clip-path="url(#clip320)" d="M2272.45 206.715 L2561.79 206.715 L2561.79 103.035 L2272.45 103.035  Z" fill="#ffffff" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2272.45,206.715 2561.79,206.715 2561.79,103.035 2272.45,103.035 2272.45,206.715 "/>
<path clip-path="url(#clip320)" d="M2298.78 175.611 L2456.71 175.611 L2456.71 134.139 L2298.78 134.139 L2298.78 175.611  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip320)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2298.78,175.611 2456.71,175.611 2456.71,134.139 2298.78,134.139 2298.78,175.611 "/>
<path clip-path="url(#clip320)" d="M2496.88 174.562 Q2495.07 179.192 2493.36 180.604 Q2491.65 182.016 2488.78 182.016 L2485.37 182.016 L2485.37 178.451 L2487.87 178.451 Q2489.63 178.451 2490.6 177.617 Q2491.58 176.784 2492.76 173.682 L2493.52 171.738 L2483.04 146.229 L2487.55 146.229 L2495.65 166.506 L2503.75 146.229 L2508.27 146.229 L2496.88 174.562 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M2515.56 168.219 L2523.2 168.219 L2523.2 141.854 L2514.89 143.52 L2514.89 139.261 L2523.15 137.595 L2527.83 137.595 L2527.83 168.219 L2535.47 168.219 L2535.47 172.155 L2515.56 172.155 L2515.56 168.219 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /></svg>
<p>(a) Distribution of all samples.</p>
</div>
</div></td>
<td style="text-align: left;"><div width="50.0%"
data-layout-align="left">
<div>
<?xml version="1.0" encoding="utf-8"?>
<svg xmlns="http://www.w3.org/2000/svg" xmlns:xlink="http://www.w3.org/1999/xlink" width="672" height="480" viewBox="0 0 2688 1920">
<defs>
  <clipPath id="clip380">
    <rect x="0" y="0" width="2688" height="1920"/>
  </clipPath>
</defs>
<path clip-path="url(#clip380)" d="M0 1920 L2688 1920 L2688 -4.26326e-14 L0 -4.26326e-14  Z" fill="#ffffff" fill-rule="evenodd" fill-opacity="1"/>
<defs>
  <clipPath id="clip381">
    <rect x="537" y="0" width="1883" height="1883"/>
  </clipPath>
</defs>
<path clip-path="url(#clip380)" d="M240.4 1720.96 L2640.76 1720.96 L2640.76 47.2441 L240.4 47.2441  Z" fill="#ffffff" fill-rule="evenodd" fill-opacity="1"/>
<defs>
  <clipPath id="clip382">
    <rect x="240" y="47" width="2401" height="1675"/>
  </clipPath>
</defs>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="240.4,1720.96 240.4,47.2441 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="1040.52,1720.96 1040.52,47.2441 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="1840.64,1720.96 1840.64,47.2441 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="2640.76,1720.96 2640.76,47.2441 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="240.4,1720.96 2640.76,1720.96 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="240.4,1423.14 2640.76,1423.14 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="240.4,1125.33 2640.76,1125.33 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="240.4,827.516 2640.76,827.516 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="240.4,529.702 2640.76,529.702 "/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:2; stroke-opacity:0.1; fill:none" points="240.4,231.889 2640.76,231.889 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,1720.96 2640.76,1720.96 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,1720.96 240.4,1702.06 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1040.52,1720.96 1040.52,1702.06 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1840.64,1720.96 1840.64,1702.06 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2640.76,1720.96 2640.76,1702.06 "/>
<path clip-path="url(#clip380)" d="M240.4 1754.18 Q236.789 1754.18 234.96 1757.74 Q233.154 1761.29 233.154 1768.42 Q233.154 1775.52 234.96 1779.09 Q236.789 1782.63 240.4 1782.63 Q244.034 1782.63 245.84 1779.09 Q247.668 1775.52 247.668 1768.42 Q247.668 1761.29 245.84 1757.74 Q244.034 1754.18 240.4 1754.18 M240.4 1750.48 Q246.21 1750.48 249.265 1755.08 Q252.344 1759.67 252.344 1768.42 Q252.344 1777.14 249.265 1781.75 Q246.21 1786.33 240.4 1786.33 Q234.59 1786.33 231.511 1781.75 Q228.455 1777.14 228.455 1768.42 Q228.455 1759.67 231.511 1755.08 Q234.59 1750.48 240.4 1750.48 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M961.572 1782.69 Q964.929 1783.4 966.804 1785.67 Q968.702 1787.94 968.702 1791.27 Q968.702 1796.39 965.183 1799.19 Q961.665 1801.99 955.183 1801.99 Q953.007 1801.99 950.693 1801.55 Q948.401 1801.14 945.947 1800.28 L945.947 1795.76 Q947.892 1796.9 950.206 1797.48 Q952.521 1798.06 955.044 1798.06 Q959.443 1798.06 961.734 1796.32 Q964.049 1794.58 964.049 1791.27 Q964.049 1788.22 961.896 1786.51 Q959.767 1784.77 955.947 1784.77 L951.919 1784.77 L951.919 1780.93 L956.132 1780.93 Q959.581 1780.93 961.41 1779.56 Q963.239 1778.17 963.239 1775.58 Q963.239 1772.92 961.341 1771.51 Q959.466 1770.07 955.947 1770.07 Q954.026 1770.07 951.827 1770.49 Q949.628 1770.9 946.989 1771.78 L946.989 1767.62 Q949.651 1766.88 951.966 1766.51 Q954.304 1766.14 956.364 1766.14 Q961.688 1766.14 964.79 1768.57 Q967.892 1770.97 967.892 1775.09 Q967.892 1777.96 966.248 1779.95 Q964.605 1781.92 961.572 1782.69 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M977.567 1795.44 L982.452 1795.44 L982.452 1801.32 L977.567 1801.32 L977.567 1795.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1002.64 1769.84 Q999.026 1769.84 997.197 1773.4 Q995.391 1776.95 995.391 1784.08 Q995.391 1791.18 997.197 1794.75 Q999.026 1798.29 1002.64 1798.29 Q1006.27 1798.29 1008.08 1794.75 Q1009.91 1791.18 1009.91 1784.08 Q1009.91 1776.95 1008.08 1773.4 Q1006.27 1769.84 1002.64 1769.84 M1002.64 1766.14 Q1008.45 1766.14 1011.5 1770.74 Q1014.58 1775.33 1014.58 1784.08 Q1014.58 1792.8 1011.5 1797.41 Q1008.45 1801.99 1002.64 1801.99 Q996.827 1801.99 993.748 1797.41 Q990.692 1792.8 990.692 1784.08 Q990.692 1775.33 993.748 1770.74 Q996.827 1766.14 1002.64 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1050.97 1775.86 L1040.39 1786.48 L1050.97 1797.06 L1048.22 1799.86 L1037.59 1789.24 L1026.97 1799.86 L1024.23 1797.06 L1034.79 1786.48 L1024.23 1775.86 L1026.97 1773.06 L1037.59 1783.68 L1048.22 1773.06 L1050.97 1775.86 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1063.33 1797.39 L1070.97 1797.39 L1070.97 1771.02 L1062.66 1772.69 L1062.66 1768.43 L1070.92 1766.76 L1075.6 1766.76 L1075.6 1797.39 L1083.24 1797.39 L1083.24 1801.32 L1063.33 1801.32 L1063.33 1797.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1102.68 1769.84 Q1099.07 1769.84 1097.24 1773.4 Q1095.44 1776.95 1095.44 1784.08 Q1095.44 1791.18 1097.24 1794.75 Q1099.07 1798.29 1102.68 1798.29 Q1106.32 1798.29 1108.12 1794.75 Q1109.95 1791.18 1109.95 1784.08 Q1109.95 1776.95 1108.12 1773.4 Q1106.32 1769.84 1102.68 1769.84 M1102.68 1766.14 Q1108.49 1766.14 1111.55 1770.74 Q1114.63 1775.33 1114.63 1784.08 Q1114.63 1792.8 1111.55 1797.41 Q1108.49 1801.99 1102.68 1801.99 Q1096.87 1801.99 1093.79 1797.41 Q1090.74 1792.8 1090.74 1784.08 Q1090.74 1775.33 1093.79 1770.74 Q1096.87 1766.14 1102.68 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1127.3 1749.14 L1117.71 1764.13 L1127.3 1764.13 L1127.3 1749.14 M1126.31 1745.83 L1131.08 1745.83 L1131.08 1764.13 L1135.09 1764.13 L1135.09 1767.29 L1131.08 1767.29 L1131.08 1773.91 L1127.3 1773.91 L1127.3 1767.29 L1114.63 1767.29 L1114.63 1763.62 L1126.31 1745.83 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1758.25 1782.18 Q1755.11 1782.18 1753.25 1784.33 Q1751.42 1786.48 1751.42 1790.23 Q1751.42 1793.96 1753.25 1796.14 Q1755.11 1798.29 1758.25 1798.29 Q1761.4 1798.29 1763.23 1796.14 Q1765.08 1793.96 1765.08 1790.23 Q1765.08 1786.48 1763.23 1784.33 Q1761.4 1782.18 1758.25 1782.18 M1767.54 1767.52 L1767.54 1771.78 Q1765.78 1770.95 1763.97 1770.51 Q1762.19 1770.07 1760.43 1770.07 Q1755.8 1770.07 1753.35 1773.2 Q1750.92 1776.32 1750.57 1782.64 Q1751.93 1780.63 1753.99 1779.56 Q1756.05 1778.47 1758.53 1778.47 Q1763.74 1778.47 1766.75 1781.64 Q1769.78 1784.79 1769.78 1790.23 Q1769.78 1795.56 1766.63 1798.77 Q1763.48 1801.99 1758.25 1801.99 Q1752.26 1801.99 1749.09 1797.41 Q1745.92 1792.8 1745.92 1784.08 Q1745.92 1775.88 1749.8 1771.02 Q1753.69 1766.14 1760.24 1766.14 Q1762 1766.14 1763.79 1766.48 Q1765.59 1766.83 1767.54 1767.52 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1777.84 1795.44 L1782.72 1795.44 L1782.72 1801.32 L1777.84 1801.32 L1777.84 1795.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1802.91 1769.84 Q1799.29 1769.84 1797.47 1773.4 Q1795.66 1776.95 1795.66 1784.08 Q1795.66 1791.18 1797.47 1794.75 Q1799.29 1798.29 1802.91 1798.29 Q1806.54 1798.29 1808.35 1794.75 Q1810.17 1791.18 1810.17 1784.08 Q1810.17 1776.95 1808.35 1773.4 Q1806.54 1769.84 1802.91 1769.84 M1802.91 1766.14 Q1808.72 1766.14 1811.77 1770.74 Q1814.85 1775.33 1814.85 1784.08 Q1814.85 1792.8 1811.77 1797.41 Q1808.72 1801.99 1802.91 1801.99 Q1797.1 1801.99 1794.02 1797.41 Q1790.96 1792.8 1790.96 1784.08 Q1790.96 1775.33 1794.02 1770.74 Q1797.1 1766.14 1802.91 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1851.24 1775.86 L1840.66 1786.48 L1851.24 1797.06 L1848.48 1799.86 L1837.86 1789.24 L1827.23 1799.86 L1824.5 1797.06 L1835.06 1786.48 L1824.5 1775.86 L1827.23 1773.06 L1837.86 1783.68 L1848.48 1773.06 L1851.24 1775.86 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1863.6 1797.39 L1871.24 1797.39 L1871.24 1771.02 L1862.93 1772.69 L1862.93 1768.43 L1871.19 1766.76 L1875.87 1766.76 L1875.87 1797.39 L1883.51 1797.39 L1883.51 1801.32 L1863.6 1801.32 L1863.6 1797.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1902.95 1769.84 Q1899.34 1769.84 1897.51 1773.4 Q1895.71 1776.95 1895.71 1784.08 Q1895.71 1791.18 1897.51 1794.75 Q1899.34 1798.29 1902.95 1798.29 Q1906.59 1798.29 1908.39 1794.75 Q1910.22 1791.18 1910.22 1784.08 Q1910.22 1776.95 1908.39 1773.4 Q1906.59 1769.84 1902.95 1769.84 M1902.95 1766.14 Q1908.76 1766.14 1911.82 1770.74 Q1914.9 1775.33 1914.9 1784.08 Q1914.9 1792.8 1911.82 1797.41 Q1908.76 1801.99 1902.95 1801.99 Q1897.14 1801.99 1894.06 1797.41 Q1891.01 1792.8 1891.01 1784.08 Q1891.01 1775.33 1894.06 1770.74 Q1897.14 1766.14 1902.95 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1927.57 1749.14 L1917.98 1764.13 L1927.57 1764.13 L1927.57 1749.14 M1926.58 1745.83 L1931.35 1745.83 L1931.35 1764.13 L1935.36 1764.13 L1935.36 1767.29 L1931.35 1767.29 L1931.35 1773.91 L1927.57 1773.91 L1927.57 1767.29 L1914.9 1767.29 L1914.9 1763.62 L1926.58 1745.83 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2548.09 1800.6 L2548.09 1796.34 Q2549.85 1797.18 2551.66 1797.62 Q2553.46 1798.06 2555.2 1798.06 Q2559.83 1798.06 2562.26 1794.95 Q2564.71 1791.83 2565.06 1785.49 Q2563.72 1787.48 2561.66 1788.54 Q2559.6 1789.61 2557.1 1789.61 Q2551.91 1789.61 2548.88 1786.48 Q2545.87 1783.33 2545.87 1777.89 Q2545.87 1772.57 2549.02 1769.35 Q2552.17 1766.14 2557.4 1766.14 Q2563.4 1766.14 2566.54 1770.74 Q2569.71 1775.33 2569.71 1784.08 Q2569.71 1792.25 2565.83 1797.13 Q2561.96 1801.99 2555.41 1801.99 Q2553.65 1801.99 2551.84 1801.64 Q2550.04 1801.3 2548.09 1800.6 M2557.4 1785.95 Q2560.55 1785.95 2562.38 1783.8 Q2564.23 1781.64 2564.23 1777.89 Q2564.23 1774.17 2562.38 1772.02 Q2560.55 1769.84 2557.4 1769.84 Q2554.25 1769.84 2552.4 1772.02 Q2550.57 1774.17 2550.57 1777.89 Q2550.57 1781.64 2552.4 1783.8 Q2554.25 1785.95 2557.4 1785.95 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2578.12 1795.44 L2583 1795.44 L2583 1801.32 L2578.12 1801.32 L2578.12 1795.44 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2603.19 1769.84 Q2599.58 1769.84 2597.75 1773.4 Q2595.94 1776.95 2595.94 1784.08 Q2595.94 1791.18 2597.75 1794.75 Q2599.58 1798.29 2603.19 1798.29 Q2606.82 1798.29 2608.63 1794.75 Q2610.46 1791.18 2610.46 1784.08 Q2610.46 1776.95 2608.63 1773.4 Q2606.82 1769.84 2603.19 1769.84 M2603.19 1766.14 Q2609 1766.14 2612.05 1770.74 Q2615.13 1775.33 2615.13 1784.08 Q2615.13 1792.8 2612.05 1797.41 Q2609 1801.99 2603.19 1801.99 Q2597.38 1801.99 2594.3 1797.41 Q2591.24 1792.8 2591.24 1784.08 Q2591.24 1775.33 2594.3 1770.74 Q2597.38 1766.14 2603.19 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2651.52 1775.86 L2640.94 1786.48 L2651.52 1797.06 L2648.77 1799.86 L2638.14 1789.24 L2627.52 1799.86 L2624.78 1797.06 L2635.34 1786.48 L2624.78 1775.86 L2627.52 1773.06 L2638.14 1783.68 L2648.77 1773.06 L2651.52 1775.86 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2663.88 1797.39 L2671.52 1797.39 L2671.52 1771.02 L2663.21 1772.69 L2663.21 1768.43 L2671.47 1766.76 L2676.15 1766.76 L2676.15 1797.39 L2683.79 1797.39 L2683.79 1801.32 L2663.88 1801.32 L2663.88 1797.39 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2703.23 1769.84 Q2699.62 1769.84 2697.79 1773.4 Q2695.99 1776.95 2695.99 1784.08 Q2695.99 1791.18 2697.79 1794.75 Q2699.62 1798.29 2703.23 1798.29 Q2706.87 1798.29 2708.67 1794.75 Q2710.5 1791.18 2710.5 1784.08 Q2710.5 1776.95 2708.67 1773.4 Q2706.87 1769.84 2703.23 1769.84 M2703.23 1766.14 Q2709.04 1766.14 2712.1 1770.74 Q2715.18 1775.33 2715.18 1784.08 Q2715.18 1792.8 2712.1 1797.41 Q2709.04 1801.99 2703.23 1801.99 Q2697.42 1801.99 2694.34 1797.41 Q2691.29 1792.8 2691.29 1784.08 Q2691.29 1775.33 2694.34 1770.74 Q2697.42 1766.14 2703.23 1766.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2727.85 1749.14 L2718.26 1764.13 L2727.85 1764.13 L2727.85 1749.14 M2726.86 1745.83 L2731.63 1745.83 L2731.63 1764.13 L2735.64 1764.13 L2735.64 1767.29 L2731.63 1767.29 L2731.63 1773.91 L2727.85 1773.91 L2727.85 1767.29 L2715.18 1767.29 L2715.18 1763.62 L2726.86 1745.83 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1027.14 1847.38 L1018.42 1871.03 L1035.89 1871.03 L1027.14 1847.38 M1023.51 1841.05 L1030.8 1841.05 L1048.91 1888.57 L1042.23 1888.57 L1037.9 1876.37 L1016.48 1876.37 L1012.15 1888.57 L1005.37 1888.57 L1023.51 1841.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1085.23 1867.05 L1085.23 1888.57 L1079.37 1888.57 L1079.37 1867.24 Q1079.37 1862.18 1077.4 1859.66 Q1075.42 1857.15 1071.48 1857.15 Q1066.74 1857.15 1064 1860.17 Q1061.26 1863.2 1061.26 1868.42 L1061.26 1888.57 L1055.37 1888.57 L1055.37 1852.92 L1061.26 1852.92 L1061.26 1858.46 Q1063.36 1855.24 1066.19 1853.65 Q1069.06 1852.06 1072.78 1852.06 Q1078.93 1852.06 1082.08 1855.88 Q1085.23 1859.66 1085.23 1867.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1126.54 1867.05 L1126.54 1888.57 L1120.69 1888.57 L1120.69 1867.24 Q1120.69 1862.18 1118.71 1859.66 Q1116.74 1857.15 1112.79 1857.15 Q1108.05 1857.15 1105.31 1860.17 Q1102.57 1863.2 1102.57 1868.42 L1102.57 1888.57 L1096.69 1888.57 L1096.69 1852.92 L1102.57 1852.92 L1102.57 1858.46 Q1104.68 1855.24 1107.51 1853.65 Q1110.37 1852.06 1114.1 1852.06 Q1120.24 1852.06 1123.39 1855.88 Q1126.54 1859.66 1126.54 1867.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1137.62 1874.5 L1137.62 1852.92 L1143.47 1852.92 L1143.47 1874.27 Q1143.47 1879.33 1145.45 1881.88 Q1147.42 1884.4 1151.37 1884.4 Q1156.11 1884.4 1158.85 1881.37 Q1161.62 1878.35 1161.62 1873.13 L1161.62 1852.92 L1167.47 1852.92 L1167.47 1888.57 L1161.62 1888.57 L1161.62 1883.09 Q1159.48 1886.34 1156.65 1887.93 Q1153.85 1889.49 1150.13 1889.49 Q1143.98 1889.49 1140.8 1885.67 Q1137.62 1881.85 1137.62 1874.5 M1152.35 1852.06 L1152.35 1852.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1195.74 1870.65 Q1188.64 1870.65 1185.9 1872.27 Q1183.16 1873.89 1183.16 1877.81 Q1183.16 1880.93 1185.2 1882.77 Q1187.27 1884.59 1190.8 1884.59 Q1195.67 1884.59 1198.6 1881.15 Q1201.56 1877.68 1201.56 1871.95 L1201.56 1870.65 L1195.74 1870.65 M1207.42 1868.23 L1207.42 1888.57 L1201.56 1888.57 L1201.56 1883.15 Q1199.56 1886.4 1196.56 1887.96 Q1193.57 1889.49 1189.24 1889.49 Q1183.77 1889.49 1180.52 1886.43 Q1177.31 1883.35 1177.31 1878.19 Q1177.31 1872.17 1181.32 1869.12 Q1185.36 1866.06 1193.35 1866.06 L1201.56 1866.06 L1201.56 1865.49 Q1201.56 1861.45 1198.89 1859.25 Q1196.25 1857.02 1191.44 1857.02 Q1188.38 1857.02 1185.49 1857.76 Q1182.59 1858.49 1179.92 1859.95 L1179.92 1854.54 Q1183.13 1853.3 1186.16 1852.69 Q1189.18 1852.06 1192.04 1852.06 Q1199.78 1852.06 1203.6 1856.07 Q1207.42 1860.08 1207.42 1868.23 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1219.48 1839.04 L1225.34 1839.04 L1225.34 1888.57 L1219.48 1888.57 L1219.48 1839.04 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1265 1846.33 L1265 1883.28 L1272.76 1883.28 Q1282.6 1883.28 1287.15 1878.83 Q1291.73 1874.37 1291.73 1864.76 Q1291.73 1855.21 1287.15 1850.78 Q1282.6 1846.33 1272.76 1846.33 L1265 1846.33 M1258.57 1841.05 L1271.78 1841.05 Q1285.59 1841.05 1292.05 1846.81 Q1298.51 1852.54 1298.51 1864.76 Q1298.51 1877.04 1292.02 1882.8 Q1285.53 1888.57 1271.78 1888.57 L1258.57 1888.57 L1258.57 1841.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1324.71 1870.65 Q1317.61 1870.65 1314.87 1872.27 Q1312.13 1873.89 1312.13 1877.81 Q1312.13 1880.93 1314.17 1882.77 Q1316.24 1884.59 1319.77 1884.59 Q1324.64 1884.59 1327.57 1881.15 Q1330.53 1877.68 1330.53 1871.95 L1330.53 1870.65 L1324.71 1870.65 M1336.39 1868.23 L1336.39 1888.57 L1330.53 1888.57 L1330.53 1883.15 Q1328.53 1886.4 1325.53 1887.96 Q1322.54 1889.49 1318.21 1889.49 Q1312.74 1889.49 1309.49 1886.43 Q1306.28 1883.35 1306.28 1878.19 Q1306.28 1872.17 1310.29 1869.12 Q1314.33 1866.06 1322.32 1866.06 L1330.53 1866.06 L1330.53 1865.49 Q1330.53 1861.45 1327.86 1859.25 Q1325.22 1857.02 1320.41 1857.02 Q1317.35 1857.02 1314.46 1857.76 Q1311.56 1858.49 1308.89 1859.95 L1308.89 1854.54 Q1312.1 1853.3 1315.13 1852.69 Q1318.15 1852.06 1321.01 1852.06 Q1328.75 1852.06 1332.57 1856.07 Q1336.39 1860.08 1336.39 1868.23 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1376.2 1859.76 Q1378.4 1855.81 1381.46 1853.94 Q1384.51 1852.06 1388.65 1852.06 Q1394.22 1852.06 1397.24 1855.97 Q1400.27 1859.86 1400.27 1867.05 L1400.27 1888.57 L1394.38 1888.57 L1394.38 1867.24 Q1394.38 1862.12 1392.56 1859.63 Q1390.75 1857.15 1387.03 1857.15 Q1382.47 1857.15 1379.83 1860.17 Q1377.19 1863.2 1377.19 1868.42 L1377.19 1888.57 L1371.3 1888.57 L1371.3 1867.24 Q1371.3 1862.08 1369.49 1859.63 Q1367.67 1857.15 1363.89 1857.15 Q1359.4 1857.15 1356.76 1860.21 Q1354.12 1863.23 1354.12 1868.42 L1354.12 1888.57 L1348.23 1888.57 L1348.23 1852.92 L1354.12 1852.92 L1354.12 1858.46 Q1356.12 1855.18 1358.92 1853.62 Q1361.72 1852.06 1365.57 1852.06 Q1369.46 1852.06 1372.16 1854.03 Q1374.9 1856 1376.2 1859.76 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1428.15 1870.65 Q1421.05 1870.65 1418.31 1872.27 Q1415.58 1873.89 1415.58 1877.81 Q1415.58 1880.93 1417.61 1882.77 Q1419.68 1884.59 1423.22 1884.59 Q1428.09 1884.59 1431.01 1881.15 Q1433.97 1877.68 1433.97 1871.95 L1433.97 1870.65 L1428.15 1870.65 M1439.83 1868.23 L1439.83 1888.57 L1433.97 1888.57 L1433.97 1883.15 Q1431.97 1886.4 1428.98 1887.96 Q1425.98 1889.49 1421.66 1889.49 Q1416.18 1889.49 1412.93 1886.43 Q1409.72 1883.35 1409.72 1878.19 Q1409.72 1872.17 1413.73 1869.12 Q1417.77 1866.06 1425.76 1866.06 L1433.97 1866.06 L1433.97 1865.49 Q1433.97 1861.45 1431.3 1859.25 Q1428.66 1857.02 1423.85 1857.02 Q1420.8 1857.02 1417.9 1857.76 Q1415 1858.49 1412.33 1859.95 L1412.33 1854.54 Q1415.54 1853.3 1418.57 1852.69 Q1421.59 1852.06 1424.46 1852.06 Q1432.19 1852.06 1436.01 1856.07 Q1439.83 1860.08 1439.83 1868.23 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1475.35 1870.33 Q1475.35 1863.96 1472.71 1860.46 Q1470.1 1856.96 1465.36 1856.96 Q1460.65 1856.96 1458 1860.46 Q1455.39 1863.96 1455.39 1870.33 Q1455.39 1876.66 1458 1880.16 Q1460.65 1883.66 1465.36 1883.66 Q1470.1 1883.66 1472.71 1880.16 Q1475.35 1876.66 1475.35 1870.33 M1481.21 1884.14 Q1481.21 1893.24 1477.16 1897.67 Q1473.12 1902.12 1464.78 1902.12 Q1461.7 1902.12 1458.96 1901.65 Q1456.22 1901.2 1453.64 1900.25 L1453.64 1894.55 Q1456.22 1895.95 1458.74 1896.62 Q1461.25 1897.29 1463.86 1897.29 Q1469.62 1897.29 1472.49 1894.26 Q1475.35 1891.27 1475.35 1885.19 L1475.35 1882.29 Q1473.54 1885.45 1470.7 1887.01 Q1467.87 1888.57 1463.92 1888.57 Q1457.37 1888.57 1453.36 1883.57 Q1449.35 1878.57 1449.35 1870.33 Q1449.35 1862.05 1453.36 1857.05 Q1457.37 1852.06 1463.92 1852.06 Q1467.87 1852.06 1470.7 1853.62 Q1473.54 1855.18 1475.35 1858.33 L1475.35 1852.92 L1481.21 1852.92 L1481.21 1884.14 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1523.76 1869.28 L1523.76 1872.14 L1496.83 1872.14 Q1497.22 1878.19 1500.46 1881.37 Q1503.74 1884.52 1509.57 1884.52 Q1512.94 1884.52 1516.09 1883.7 Q1519.27 1882.87 1522.39 1881.21 L1522.39 1886.75 Q1519.24 1888.09 1515.93 1888.79 Q1512.62 1889.49 1509.22 1889.49 Q1500.69 1889.49 1495.69 1884.52 Q1490.72 1879.56 1490.72 1871.09 Q1490.72 1862.34 1495.43 1857.21 Q1500.18 1852.06 1508.2 1852.06 Q1515.39 1852.06 1519.56 1856.7 Q1523.76 1861.32 1523.76 1869.28 M1517.91 1867.56 Q1517.84 1862.75 1515.2 1859.89 Q1512.59 1857.02 1508.26 1857.02 Q1503.36 1857.02 1500.4 1859.79 Q1497.47 1862.56 1497.03 1867.59 L1517.91 1867.56 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1556.83 1858.33 L1556.83 1839.04 L1562.69 1839.04 L1562.69 1888.57 L1556.83 1888.57 L1556.83 1883.22 Q1554.99 1886.4 1552.15 1887.96 Q1549.35 1889.49 1545.41 1889.49 Q1538.94 1889.49 1534.87 1884.33 Q1530.83 1879.18 1530.83 1870.77 Q1530.83 1862.37 1534.87 1857.21 Q1538.94 1852.06 1545.41 1852.06 Q1549.35 1852.06 1552.15 1853.62 Q1554.99 1855.15 1556.83 1858.33 M1536.88 1870.77 Q1536.88 1877.23 1539.52 1880.93 Q1542.19 1884.59 1546.84 1884.59 Q1551.48 1884.59 1554.16 1880.93 Q1556.83 1877.23 1556.83 1870.77 Q1556.83 1864.31 1554.16 1860.65 Q1551.48 1856.96 1546.84 1856.96 Q1542.19 1856.96 1539.52 1860.65 Q1536.88 1864.31 1536.88 1870.77 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1607.98 1888.57 L1589.84 1841.05 L1596.55 1841.05 L1611.61 1881.05 L1626.7 1841.05 L1633.38 1841.05 L1615.27 1888.57 L1607.98 1888.57 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1651.2 1870.65 Q1644.11 1870.65 1641.37 1872.27 Q1638.63 1873.89 1638.63 1877.81 Q1638.63 1880.93 1640.67 1882.77 Q1642.74 1884.59 1646.27 1884.59 Q1651.14 1884.59 1654.07 1881.15 Q1657.03 1877.68 1657.03 1871.95 L1657.03 1870.65 L1651.2 1870.65 M1662.88 1868.23 L1662.88 1888.57 L1657.03 1888.57 L1657.03 1883.15 Q1655.02 1886.4 1652.03 1887.96 Q1649.04 1889.49 1644.71 1889.49 Q1639.24 1889.49 1635.99 1886.43 Q1632.77 1883.35 1632.77 1878.19 Q1632.77 1872.17 1636.78 1869.12 Q1640.83 1866.06 1648.82 1866.06 L1657.03 1866.06 L1657.03 1865.49 Q1657.03 1861.45 1654.35 1859.25 Q1651.71 1857.02 1646.91 1857.02 Q1643.85 1857.02 1640.95 1857.76 Q1638.06 1858.49 1635.38 1859.95 L1635.38 1854.54 Q1638.6 1853.3 1641.62 1852.69 Q1644.65 1852.06 1647.51 1852.06 Q1655.25 1852.06 1659.06 1856.07 Q1662.88 1860.08 1662.88 1868.23 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1674.95 1839.04 L1680.8 1839.04 L1680.8 1888.57 L1674.95 1888.57 L1674.95 1839.04 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1692.45 1874.5 L1692.45 1852.92 L1698.31 1852.92 L1698.31 1874.27 Q1698.31 1879.33 1700.28 1881.88 Q1702.26 1884.4 1706.2 1884.4 Q1710.95 1884.4 1713.68 1881.37 Q1716.45 1878.35 1716.45 1873.13 L1716.45 1852.92 L1722.31 1852.92 L1722.31 1888.57 L1716.45 1888.57 L1716.45 1883.09 Q1714.32 1886.34 1711.49 1887.93 Q1708.69 1889.49 1704.96 1889.49 Q1698.82 1889.49 1695.64 1885.67 Q1692.45 1881.85 1692.45 1874.5 M1707.19 1852.06 L1707.19 1852.06 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1764.86 1869.28 L1764.86 1872.14 L1737.94 1872.14 Q1738.32 1878.19 1741.56 1881.37 Q1744.84 1884.52 1750.67 1884.52 Q1754.04 1884.52 1757.19 1883.7 Q1760.38 1882.87 1763.49 1881.21 L1763.49 1886.75 Q1760.34 1888.09 1757.03 1888.79 Q1753.72 1889.49 1750.32 1889.49 Q1741.79 1889.49 1736.79 1884.52 Q1731.82 1879.56 1731.82 1871.09 Q1731.82 1862.34 1736.54 1857.21 Q1741.28 1852.06 1749.3 1852.06 Q1756.49 1852.06 1760.66 1856.7 Q1764.86 1861.32 1764.86 1869.28 M1759.01 1867.56 Q1758.94 1862.75 1756.3 1859.89 Q1753.69 1857.02 1749.36 1857.02 Q1744.46 1857.02 1741.5 1859.79 Q1738.57 1862.56 1738.13 1867.59 L1759.01 1867.56 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1809.26 1839.1 Q1805 1846.42 1802.93 1853.59 Q1800.86 1860.75 1800.86 1868.1 Q1800.86 1875.45 1802.93 1882.68 Q1805.03 1889.87 1809.26 1897.16 L1804.17 1897.16 Q1799.4 1889.68 1797.01 1882.45 Q1794.65 1875.23 1794.65 1868.1 Q1794.65 1861 1797.01 1853.81 Q1799.36 1846.62 1804.17 1839.1 L1809.26 1839.1 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1836.51 1898.15 L1833.33 1898.15 L1833.29 1888.57 Q1829.95 1888.5 1826.61 1887.8 Q1823.27 1887.07 1819.89 1885.64 L1819.89 1879.91 Q1823.14 1881.94 1826.45 1883 Q1829.79 1884.01 1833.33 1884.05 L1833.33 1869.53 Q1826.29 1868.39 1823.08 1865.65 Q1819.89 1862.91 1819.89 1858.14 Q1819.89 1852.95 1823.36 1849.96 Q1826.83 1846.97 1833.33 1846.52 L1833.33 1839.04 L1836.51 1839.04 L1836.51 1846.42 Q1839.47 1846.55 1842.24 1847.06 Q1845.01 1847.54 1847.65 1848.4 L1847.65 1853.97 Q1845.01 1852.63 1842.21 1851.9 Q1839.44 1851.17 1836.51 1851.04 L1836.51 1864.63 Q1843.73 1865.74 1847.14 1868.61 Q1850.55 1871.47 1850.55 1876.44 Q1850.55 1881.82 1846.92 1884.94 Q1843.32 1888.02 1836.51 1888.5 L1836.51 1898.15 M1833.33 1864.06 L1833.33 1851.01 Q1829.63 1851.42 1827.69 1853.11 Q1825.75 1854.8 1825.75 1857.6 Q1825.75 1860.33 1827.53 1861.86 Q1829.35 1863.39 1833.33 1864.06 M1836.51 1870.17 L1836.51 1883.95 Q1840.55 1883.41 1842.59 1881.66 Q1844.66 1879.91 1844.66 1877.04 Q1844.66 1874.24 1842.68 1872.59 Q1840.74 1870.93 1836.51 1870.17 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M1861.18 1839.1 L1866.27 1839.1 Q1871.04 1846.62 1873.4 1853.81 Q1875.79 1861 1875.79 1868.1 Q1875.79 1875.23 1873.4 1882.45 Q1871.04 1889.68 1866.27 1897.16 L1861.18 1897.16 Q1865.41 1889.87 1867.48 1882.68 Q1869.58 1875.45 1869.58 1868.1 Q1869.58 1860.75 1867.48 1853.59 Q1865.41 1846.42 1861.18 1839.1 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,1720.96 240.4,47.2441 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,1720.96 259.297,1720.96 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,1423.14 259.297,1423.14 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,1125.33 259.297,1125.33 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,827.516 259.297,827.516 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,529.702 259.297,529.702 "/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="240.4,231.889 259.297,231.889 "/>
<path clip-path="url(#clip380)" d="M188.135 1706.76 Q184.524 1706.76 182.696 1710.32 Q180.89 1713.86 180.89 1720.99 Q180.89 1728.1 182.696 1731.66 Q184.524 1735.2 188.135 1735.2 Q191.77 1735.2 193.575 1731.66 Q195.404 1728.1 195.404 1720.99 Q195.404 1713.86 193.575 1710.32 Q191.77 1706.76 188.135 1706.76 M188.135 1703.05 Q193.946 1703.05 197.001 1707.66 Q200.08 1712.24 200.08 1720.99 Q200.08 1729.72 197.001 1734.32 Q193.946 1738.91 188.135 1738.91 Q182.325 1738.91 179.247 1734.32 Q176.191 1729.72 176.191 1720.99 Q176.191 1712.24 179.247 1707.66 Q182.325 1703.05 188.135 1703.05 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M148.02 1405.86 L166.376 1405.86 L166.376 1409.8 L152.302 1409.8 L152.302 1418.27 Q153.321 1417.92 154.339 1417.76 Q155.358 1417.58 156.376 1417.58 Q162.163 1417.58 165.543 1420.75 Q168.922 1423.92 168.922 1429.33 Q168.922 1434.91 165.45 1438.02 Q161.978 1441.09 155.659 1441.09 Q153.483 1441.09 151.214 1440.72 Q148.969 1440.35 146.562 1439.61 L146.562 1434.91 Q148.645 1436.05 150.867 1436.6 Q153.089 1437.16 155.566 1437.16 Q159.571 1437.16 161.909 1435.05 Q164.247 1432.95 164.247 1429.33 Q164.247 1425.72 161.909 1423.62 Q159.571 1421.51 155.566 1421.51 Q153.691 1421.51 151.816 1421.93 Q149.964 1422.34 148.02 1423.22 L148.02 1405.86 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M188.135 1408.94 Q184.524 1408.94 182.696 1412.51 Q180.89 1416.05 180.89 1423.18 Q180.89 1430.28 182.696 1433.85 Q184.524 1437.39 188.135 1437.39 Q191.77 1437.39 193.575 1433.85 Q195.404 1430.28 195.404 1423.18 Q195.404 1416.05 193.575 1412.51 Q191.77 1408.94 188.135 1408.94 M188.135 1405.24 Q193.946 1405.24 197.001 1409.84 Q200.08 1414.43 200.08 1423.18 Q200.08 1431.9 197.001 1436.51 Q193.946 1441.09 188.135 1441.09 Q182.325 1441.09 179.247 1436.51 Q176.191 1431.9 176.191 1423.18 Q176.191 1414.43 179.247 1409.84 Q182.325 1405.24 188.135 1405.24 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M118.622 1138.67 L126.261 1138.67 L126.261 1112.31 L117.951 1113.98 L117.951 1109.72 L126.214 1108.05 L130.89 1108.05 L130.89 1138.67 L138.529 1138.67 L138.529 1142.61 L118.622 1142.61 L118.622 1138.67 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M157.973 1111.13 Q154.362 1111.13 152.534 1114.69 Q150.728 1118.23 150.728 1125.36 Q150.728 1132.47 152.534 1136.04 Q154.362 1139.58 157.973 1139.58 Q161.608 1139.58 163.413 1136.04 Q165.242 1132.47 165.242 1125.36 Q165.242 1118.23 163.413 1114.69 Q161.608 1111.13 157.973 1111.13 M157.973 1107.42 Q163.784 1107.42 166.839 1112.03 Q169.918 1116.61 169.918 1125.36 Q169.918 1134.09 166.839 1138.7 Q163.784 1143.28 157.973 1143.28 Q152.163 1143.28 149.085 1138.7 Q146.029 1134.09 146.029 1125.36 Q146.029 1116.61 149.085 1112.03 Q152.163 1107.42 157.973 1107.42 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M188.135 1111.13 Q184.524 1111.13 182.696 1114.69 Q180.89 1118.23 180.89 1125.36 Q180.89 1132.47 182.696 1136.04 Q184.524 1139.58 188.135 1139.58 Q191.77 1139.58 193.575 1136.04 Q195.404 1132.47 195.404 1125.36 Q195.404 1118.23 193.575 1114.69 Q191.77 1111.13 188.135 1111.13 M188.135 1107.42 Q193.946 1107.42 197.001 1112.03 Q200.08 1116.61 200.08 1125.36 Q200.08 1134.09 197.001 1138.7 Q193.946 1143.28 188.135 1143.28 Q182.325 1143.28 179.247 1138.7 Q176.191 1134.09 176.191 1125.36 Q176.191 1116.61 179.247 1112.03 Q182.325 1107.42 188.135 1107.42 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M118.622 840.861 L126.261 840.861 L126.261 814.495 L117.951 816.162 L117.951 811.902 L126.214 810.236 L130.89 810.236 L130.89 840.861 L138.529 840.861 L138.529 844.796 L118.622 844.796 L118.622 840.861 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M148.02 810.236 L166.376 810.236 L166.376 814.171 L152.302 814.171 L152.302 822.643 Q153.321 822.296 154.339 822.134 Q155.358 821.949 156.376 821.949 Q162.163 821.949 165.543 825.12 Q168.922 828.291 168.922 833.708 Q168.922 839.286 165.45 842.388 Q161.978 845.467 155.659 845.467 Q153.483 845.467 151.214 845.097 Q148.969 844.726 146.562 843.985 L146.562 839.286 Q148.645 840.421 150.867 840.976 Q153.089 841.532 155.566 841.532 Q159.571 841.532 161.909 839.425 Q164.247 837.319 164.247 833.708 Q164.247 830.097 161.909 827.99 Q159.571 825.884 155.566 825.884 Q153.691 825.884 151.816 826.3 Q149.964 826.717 148.02 827.597 L148.02 810.236 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M188.135 813.314 Q184.524 813.314 182.696 816.879 Q180.89 820.421 180.89 827.55 Q180.89 834.657 182.696 838.222 Q184.524 841.763 188.135 841.763 Q191.77 841.763 193.575 838.222 Q195.404 834.657 195.404 827.55 Q195.404 820.421 193.575 816.879 Q191.77 813.314 188.135 813.314 M188.135 809.611 Q193.946 809.611 197.001 814.217 Q200.08 818.8 200.08 827.55 Q200.08 836.277 197.001 840.884 Q193.946 845.467 188.135 845.467 Q182.325 845.467 179.247 840.884 Q176.191 836.277 176.191 827.55 Q176.191 818.8 179.247 814.217 Q182.325 809.611 188.135 809.611 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M121.839 543.047 L138.159 543.047 L138.159 546.982 L116.214 546.982 L116.214 543.047 Q118.876 540.292 123.46 535.663 Q128.066 531.01 129.247 529.667 Q131.492 527.144 132.372 525.408 Q133.275 523.649 133.275 521.959 Q133.275 519.204 131.33 517.468 Q129.409 515.732 126.307 515.732 Q124.108 515.732 121.654 516.496 Q119.224 517.26 116.446 518.811 L116.446 514.089 Q119.27 512.954 121.724 512.376 Q124.177 511.797 126.214 511.797 Q131.585 511.797 134.779 514.482 Q137.974 517.167 137.974 521.658 Q137.974 523.788 137.163 525.709 Q136.376 527.607 134.27 530.2 Q133.691 530.871 130.589 534.089 Q127.488 537.283 121.839 543.047 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M157.973 515.501 Q154.362 515.501 152.534 519.066 Q150.728 522.607 150.728 529.737 Q150.728 536.843 152.534 540.408 Q154.362 543.95 157.973 543.95 Q161.608 543.95 163.413 540.408 Q165.242 536.843 165.242 529.737 Q165.242 522.607 163.413 519.066 Q161.608 515.501 157.973 515.501 M157.973 511.797 Q163.784 511.797 166.839 516.404 Q169.918 520.987 169.918 529.737 Q169.918 538.464 166.839 543.07 Q163.784 547.653 157.973 547.653 Q152.163 547.653 149.085 543.07 Q146.029 538.464 146.029 529.737 Q146.029 520.987 149.085 516.404 Q152.163 511.797 157.973 511.797 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M188.135 515.501 Q184.524 515.501 182.696 519.066 Q180.89 522.607 180.89 529.737 Q180.89 536.843 182.696 540.408 Q184.524 543.95 188.135 543.95 Q191.77 543.95 193.575 540.408 Q195.404 536.843 195.404 529.737 Q195.404 522.607 193.575 519.066 Q191.77 515.501 188.135 515.501 M188.135 511.797 Q193.946 511.797 197.001 516.404 Q200.08 520.987 200.08 529.737 Q200.08 538.464 197.001 543.07 Q193.946 547.653 188.135 547.653 Q182.325 547.653 179.247 543.07 Q176.191 538.464 176.191 529.737 Q176.191 520.987 179.247 516.404 Q182.325 511.797 188.135 511.797 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M121.839 245.233 L138.159 245.233 L138.159 249.169 L116.214 249.169 L116.214 245.233 Q118.876 242.479 123.46 237.849 Q128.066 233.196 129.247 231.854 Q131.492 229.331 132.372 227.595 Q133.275 225.835 133.275 224.146 Q133.275 221.391 131.33 219.655 Q129.409 217.919 126.307 217.919 Q124.108 217.919 121.654 218.683 Q119.224 219.446 116.446 220.997 L116.446 216.275 Q119.27 215.141 121.724 214.562 Q124.177 213.984 126.214 213.984 Q131.585 213.984 134.779 216.669 Q137.974 219.354 137.974 223.845 Q137.974 225.974 137.163 227.895 Q136.376 229.794 134.27 232.386 Q133.691 233.057 130.589 236.275 Q127.488 239.469 121.839 245.233 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M148.02 214.609 L166.376 214.609 L166.376 218.544 L152.302 218.544 L152.302 227.016 Q153.321 226.669 154.339 226.507 Q155.358 226.321 156.376 226.321 Q162.163 226.321 165.543 229.493 Q168.922 232.664 168.922 238.081 Q168.922 243.659 165.45 246.761 Q161.978 249.84 155.659 249.84 Q153.483 249.84 151.214 249.469 Q148.969 249.099 146.562 248.358 L146.562 243.659 Q148.645 244.794 150.867 245.349 Q153.089 245.905 155.566 245.905 Q159.571 245.905 161.909 243.798 Q164.247 241.692 164.247 238.081 Q164.247 234.47 161.909 232.363 Q159.571 230.257 155.566 230.257 Q153.691 230.257 151.816 230.673 Q149.964 231.09 148.02 231.97 L148.02 214.609 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M188.135 217.687 Q184.524 217.687 182.696 221.252 Q180.89 224.794 180.89 231.923 Q180.89 239.03 182.696 242.594 Q184.524 246.136 188.135 246.136 Q191.77 246.136 193.575 242.594 Q195.404 239.03 195.404 231.923 Q195.404 224.794 193.575 221.252 Q191.77 217.687 188.135 217.687 M188.135 213.984 Q193.946 213.984 197.001 218.59 Q200.08 223.173 200.08 231.923 Q200.08 240.65 197.001 245.256 Q193.946 249.84 188.135 249.84 Q182.325 249.84 179.247 245.256 Q176.191 240.65 176.191 231.923 Q176.191 223.173 179.247 218.59 Q182.325 213.984 188.135 213.984 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M17.7787 939.959 L24.5582 939.959 Q21.5345 943.206 20.0386 946.898 Q18.5426 950.558 18.5426 954.696 Q18.5426 962.844 23.5397 967.173 Q28.5049 971.501 37.9262 971.501 Q47.3156 971.501 52.3127 967.173 Q57.2779 962.844 57.2779 954.696 Q57.2779 950.558 55.782 946.898 Q54.2861 943.206 51.2623 939.959 L57.9782 939.959 Q60.2698 943.333 61.4156 947.121 Q62.5615 950.877 62.5615 955.078 Q62.5615 965.868 55.973 972.074 Q49.3526 978.281 37.9262 978.281 Q26.4679 978.281 19.8794 972.074 Q13.2591 965.868 13.2591 955.078 Q13.2591 950.813 14.4049 947.057 Q15.5189 943.269 17.7787 939.959 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M30.0964 916.47 Q30.0964 921.18 33.7885 923.918 Q37.4488 926.655 43.8463 926.655 Q50.2438 926.655 53.9359 923.95 Q57.5962 921.212 57.5962 916.47 Q57.5962 911.791 53.9041 909.054 Q50.212 906.317 43.8463 906.317 Q37.5124 906.317 33.8203 909.054 Q30.0964 911.791 30.0964 916.47 M25.1311 916.47 Q25.1311 908.831 30.0964 904.471 Q35.0616 900.11 43.8463 900.11 Q52.5991 900.11 57.5962 904.471 Q62.5615 908.831 62.5615 916.47 Q62.5615 924.141 57.5962 928.501 Q52.5991 932.83 43.8463 932.83 Q35.0616 932.83 30.0964 928.501 Q25.1311 924.141 25.1311 916.47 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M47.5702 891.007 L25.9905 891.007 L25.9905 885.151 L47.3474 885.151 Q52.4082 885.151 54.9545 883.177 Q57.4689 881.204 57.4689 877.257 Q57.4689 872.515 54.4452 869.777 Q51.4215 867.008 46.2016 867.008 L25.9905 867.008 L25.9905 861.152 L61.6384 861.152 L61.6384 867.008 L56.1639 867.008 Q59.4104 869.141 61.0019 871.974 Q62.5615 874.774 62.5615 878.498 Q62.5615 884.641 58.742 887.824 Q54.9226 891.007 47.5702 891.007 M25.1311 876.27 L25.1311 876.27 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M40.1224 819.457 L61.6384 819.457 L61.6384 825.313 L40.3133 825.313 Q35.2526 825.313 32.7381 827.286 Q30.2237 829.26 30.2237 833.206 Q30.2237 837.949 33.2474 840.686 Q36.2711 843.423 41.491 843.423 L61.6384 843.423 L61.6384 849.312 L25.9905 849.312 L25.9905 843.423 L31.5287 843.423 Q28.314 841.323 26.7225 838.49 Q25.1311 835.625 25.1311 831.901 Q25.1311 825.759 28.9505 822.608 Q32.7381 819.457 40.1224 819.457 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M15.869 801.983 L25.9905 801.983 L25.9905 789.92 L30.542 789.92 L30.542 801.983 L49.8937 801.983 Q54.2542 801.983 55.4955 800.805 Q56.7368 799.595 56.7368 795.935 L56.7368 789.92 L61.6384 789.92 L61.6384 795.935 Q61.6384 802.715 59.124 805.293 Q56.5777 807.871 49.8937 807.871 L30.542 807.871 L30.542 812.168 L25.9905 812.168 L25.9905 807.871 L15.869 807.871 L15.869 801.983 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip382)" d="M1040.52 47.2441 L1040.52 1720.96 L1093.86 1720.96 L1093.86 47.2441 L1040.52 47.2441 L1040.52 47.2441  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1040.52,47.2441 1040.52,1720.96 1093.86,1720.96 1093.86,47.2441 1040.52,47.2441 "/>
<path clip-path="url(#clip382)" d="M1093.86 225.932 L1093.86 1720.96 L1147.2 1720.96 L1147.2 225.932 L1093.86 225.932 L1093.86 225.932  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1093.86,225.932 1093.86,1720.96 1147.2,1720.96 1147.2,225.932 1093.86,225.932 "/>
<path clip-path="url(#clip382)" d="M1147.2 756.04 L1147.2 1720.96 L1200.54 1720.96 L1200.54 756.04 L1147.2 756.04 L1147.2 756.04  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1147.2,756.04 1147.2,1720.96 1200.54,1720.96 1200.54,756.04 1147.2,756.04 "/>
<path clip-path="url(#clip382)" d="M1200.54 756.04 L1200.54 1720.96 L1253.88 1720.96 L1253.88 756.04 L1200.54 756.04 L1200.54 756.04  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1200.54,756.04 1200.54,1720.96 1253.88,1720.96 1253.88,756.04 1200.54,756.04 "/>
<path clip-path="url(#clip382)" d="M1253.88 1041.94 L1253.88 1720.96 L1307.22 1720.96 L1307.22 1041.94 L1253.88 1041.94 L1253.88 1041.94  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1253.88,1041.94 1253.88,1720.96 1307.22,1720.96 1307.22,1041.94 1253.88,1041.94 "/>
<path clip-path="url(#clip382)" d="M1307.22 1214.67 L1307.22 1720.96 L1360.57 1720.96 L1360.57 1214.67 L1307.22 1214.67 L1307.22 1214.67  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1307.22,1214.67 1307.22,1720.96 1360.57,1720.96 1360.57,1214.67 1307.22,1214.67 "/>
<path clip-path="url(#clip382)" d="M1360.57 1232.54 L1360.57 1720.96 L1413.91 1720.96 L1413.91 1232.54 L1360.57 1232.54 L1360.57 1232.54  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1360.57,1232.54 1360.57,1720.96 1413.91,1720.96 1413.91,1232.54 1360.57,1232.54 "/>
<path clip-path="url(#clip382)" d="M1413.91 1321.89 L1413.91 1720.96 L1467.25 1720.96 L1467.25 1321.89 L1413.91 1321.89 L1413.91 1321.89  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1413.91,1321.89 1413.91,1720.96 1467.25,1720.96 1467.25,1321.89 1413.91,1321.89 "/>
<path clip-path="url(#clip382)" d="M1467.25 1464.84 L1467.25 1720.96 L1520.59 1720.96 L1520.59 1464.84 L1467.25 1464.84 L1467.25 1464.84  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1467.25,1464.84 1467.25,1720.96 1520.59,1720.96 1520.59,1464.84 1467.25,1464.84 "/>
<path clip-path="url(#clip382)" d="M1520.59 1548.22 L1520.59 1720.96 L1573.93 1720.96 L1573.93 1548.22 L1520.59 1548.22 L1520.59 1548.22  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1520.59,1548.22 1520.59,1720.96 1573.93,1720.96 1573.93,1548.22 1520.59,1548.22 "/>
<path clip-path="url(#clip382)" d="M1573.93 1536.31 L1573.93 1720.96 L1627.27 1720.96 L1627.27 1536.31 L1573.93 1536.31 L1573.93 1536.31  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1573.93,1536.31 1573.93,1720.96 1627.27,1720.96 1627.27,1536.31 1573.93,1536.31 "/>
<path clip-path="url(#clip382)" d="M1627.27 1572.05 L1627.27 1720.96 L1680.61 1720.96 L1680.61 1572.05 L1627.27 1572.05 L1627.27 1572.05  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1627.27,1572.05 1627.27,1720.96 1680.61,1720.96 1680.61,1572.05 1627.27,1572.05 "/>
<path clip-path="url(#clip382)" d="M1680.61 1595.87 L1680.61 1720.96 L1733.95 1720.96 L1733.95 1595.87 L1680.61 1595.87 L1680.61 1595.87  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1680.61,1595.87 1680.61,1720.96 1733.95,1720.96 1733.95,1595.87 1680.61,1595.87 "/>
<path clip-path="url(#clip382)" d="M1733.95 1589.92 L1733.95 1720.96 L1787.3 1720.96 L1787.3 1589.92 L1733.95 1589.92 L1733.95 1589.92  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1733.95,1589.92 1733.95,1720.96 1787.3,1720.96 1787.3,1589.92 1733.95,1589.92 "/>
<path clip-path="url(#clip382)" d="M1787.3 1619.7 L1787.3 1720.96 L1840.64 1720.96 L1840.64 1619.7 L1787.3 1619.7 L1787.3 1619.7  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1787.3,1619.7 1787.3,1720.96 1840.64,1720.96 1840.64,1619.7 1787.3,1619.7 "/>
<path clip-path="url(#clip382)" d="M1840.64 1589.92 L1840.64 1720.96 L1893.98 1720.96 L1893.98 1589.92 L1840.64 1589.92 L1840.64 1589.92  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1840.64,1589.92 1840.64,1720.96 1893.98,1720.96 1893.98,1589.92 1840.64,1589.92 "/>
<path clip-path="url(#clip382)" d="M1893.98 1637.57 L1893.98 1720.96 L1947.32 1720.96 L1947.32 1637.57 L1893.98 1637.57 L1893.98 1637.57  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1893.98,1637.57 1893.98,1720.96 1947.32,1720.96 1947.32,1637.57 1893.98,1637.57 "/>
<path clip-path="url(#clip382)" d="M1947.32 1655.44 L1947.32 1720.96 L2000.66 1720.96 L2000.66 1655.44 L1947.32 1655.44 L1947.32 1655.44  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="1947.32,1655.44 1947.32,1720.96 2000.66,1720.96 2000.66,1655.44 1947.32,1655.44 "/>
<path clip-path="url(#clip382)" d="M2000.66 1679.26 L2000.66 1720.96 L2054 1720.96 L2054 1679.26 L2000.66 1679.26 L2000.66 1679.26  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2000.66,1679.26 2000.66,1720.96 2054,1720.96 2054,1679.26 2000.66,1679.26 "/>
<path clip-path="url(#clip382)" d="M2054 1673.31 L2054 1720.96 L2107.34 1720.96 L2107.34 1673.31 L2054 1673.31 L2054 1673.31  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2054,1673.31 2054,1720.96 2107.34,1720.96 2107.34,1673.31 2054,1673.31 "/>
<path clip-path="url(#clip382)" d="M2107.34 1697.13 L2107.34 1720.96 L2160.68 1720.96 L2160.68 1697.13 L2107.34 1697.13 L2107.34 1697.13  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2107.34,1697.13 2107.34,1720.96 2160.68,1720.96 2160.68,1697.13 2107.34,1697.13 "/>
<path clip-path="url(#clip382)" d="M2160.68 1703.09 L2160.68 1720.96 L2214.03 1720.96 L2214.03 1703.09 L2160.68 1703.09 L2160.68 1703.09  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2160.68,1703.09 2160.68,1720.96 2214.03,1720.96 2214.03,1703.09 2160.68,1703.09 "/>
<path clip-path="url(#clip382)" d="M2214.03 1703.09 L2214.03 1720.96 L2267.37 1720.96 L2267.37 1703.09 L2214.03 1703.09 L2214.03 1703.09  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2214.03,1703.09 2214.03,1720.96 2267.37,1720.96 2267.37,1703.09 2214.03,1703.09 "/>
<path clip-path="url(#clip382)" d="M2267.37 1697.13 L2267.37 1720.96 L2320.71 1720.96 L2320.71 1697.13 L2267.37 1697.13 L2267.37 1697.13  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2267.37,1697.13 2267.37,1720.96 2320.71,1720.96 2320.71,1697.13 2267.37,1697.13 "/>
<path clip-path="url(#clip382)" d="M2320.71 1697.13 L2320.71 1720.96 L2374.05 1720.96 L2374.05 1697.13 L2320.71 1697.13 L2320.71 1697.13  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2320.71,1697.13 2320.71,1720.96 2374.05,1720.96 2374.05,1697.13 2320.71,1697.13 "/>
<path clip-path="url(#clip382)" d="M2374.05 1709.04 L2374.05 1720.96 L2427.39 1720.96 L2427.39 1709.04 L2374.05 1709.04 L2374.05 1709.04  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2374.05,1709.04 2374.05,1720.96 2427.39,1720.96 2427.39,1709.04 2374.05,1709.04 "/>
<path clip-path="url(#clip382)" d="M2427.39 1709.04 L2427.39 1720.96 L2480.73 1720.96 L2480.73 1709.04 L2427.39 1709.04 L2427.39 1709.04  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2427.39,1709.04 2427.39,1720.96 2480.73,1720.96 2480.73,1709.04 2427.39,1709.04 "/>
<path clip-path="url(#clip382)" d="M2480.73 1715 L2480.73 1720.96 L2534.07 1720.96 L2534.07 1715 L2480.73 1715 L2480.73 1715  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2480.73,1715 2480.73,1720.96 2534.07,1720.96 2534.07,1715 2480.73,1715 "/>
<path clip-path="url(#clip382)" d="M2534.07 1703.09 L2534.07 1720.96 L2587.41 1720.96 L2587.41 1703.09 L2534.07 1703.09 L2534.07 1703.09  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2534.07,1703.09 2534.07,1720.96 2587.41,1720.96 2587.41,1703.09 2534.07,1703.09 "/>
<path clip-path="url(#clip382)" d="M2587.41 1697.13 L2587.41 1720.96 L2640.76 1720.96 L2640.76 1697.13 L2587.41 1697.13 L2587.41 1697.13  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2587.41,1697.13 2587.41,1720.96 2640.76,1720.96 2640.76,1697.13 2587.41,1697.13 "/>
<path clip-path="url(#clip382)" d="M2640.76 1720.96 L2640.76 1720.96 L2694.1 1720.96 L2694.1 1720.96 L2640.76 1720.96 L2640.76 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2640.76,1720.96 2640.76,1720.96 2694.1,1720.96 2640.76,1720.96 "/>
<path clip-path="url(#clip382)" d="M2694.1 1715 L2694.1 1720.96 L2747.44 1720.96 L2747.44 1715 L2694.1 1715 L2694.1 1715  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2694.1,1715 2694.1,1720.96 2747.44,1720.96 2747.44,1715 2694.1,1715 "/>
<path clip-path="url(#clip382)" d="M2747.44 1709.04 L2747.44 1720.96 L2800.78 1720.96 L2800.78 1709.04 L2747.44 1709.04 L2747.44 1709.04  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2747.44,1709.04 2747.44,1720.96 2800.78,1720.96 2800.78,1709.04 2747.44,1709.04 "/>
<path clip-path="url(#clip382)" d="M2800.78 1720.96 L2800.78 1720.96 L2854.12 1720.96 L2854.12 1720.96 L2800.78 1720.96 L2800.78 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2800.78,1720.96 2800.78,1720.96 2854.12,1720.96 2800.78,1720.96 "/>
<path clip-path="url(#clip382)" d="M2854.12 1720.96 L2854.12 1720.96 L2907.46 1720.96 L2907.46 1720.96 L2854.12 1720.96 L2854.12 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2854.12,1720.96 2854.12,1720.96 2907.46,1720.96 2854.12,1720.96 "/>
<path clip-path="url(#clip382)" d="M2907.46 1720.96 L2907.46 1720.96 L2960.8 1720.96 L2960.8 1720.96 L2907.46 1720.96 L2907.46 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2907.46,1720.96 2907.46,1720.96 2960.8,1720.96 2907.46,1720.96 "/>
<path clip-path="url(#clip382)" d="M2960.8 1720.96 L2960.8 1720.96 L3014.14 1720.96 L3014.14 1720.96 L2960.8 1720.96 L2960.8 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2960.8,1720.96 2960.8,1720.96 3014.14,1720.96 2960.8,1720.96 "/>
<path clip-path="url(#clip382)" d="M3014.14 1720.96 L3014.14 1720.96 L3067.49 1720.96 L3067.49 1720.96 L3014.14 1720.96 L3014.14 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3014.14,1720.96 3014.14,1720.96 3067.49,1720.96 3014.14,1720.96 "/>
<path clip-path="url(#clip382)" d="M3067.49 1720.96 L3067.49 1720.96 L3120.83 1720.96 L3120.83 1720.96 L3067.49 1720.96 L3067.49 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3067.49,1720.96 3067.49,1720.96 3120.83,1720.96 3067.49,1720.96 "/>
<path clip-path="url(#clip382)" d="M3120.83 1720.96 L3120.83 1720.96 L3174.17 1720.96 L3174.17 1720.96 L3120.83 1720.96 L3120.83 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3120.83,1720.96 3120.83,1720.96 3174.17,1720.96 3120.83,1720.96 "/>
<path clip-path="url(#clip382)" d="M3174.17 1720.96 L3174.17 1720.96 L3227.51 1720.96 L3227.51 1720.96 L3174.17 1720.96 L3174.17 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3174.17,1720.96 3174.17,1720.96 3227.51,1720.96 3174.17,1720.96 "/>
<path clip-path="url(#clip382)" d="M3227.51 1715 L3227.51 1720.96 L3280.85 1720.96 L3280.85 1715 L3227.51 1715 L3227.51 1715  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3227.51,1715 3227.51,1720.96 3280.85,1720.96 3280.85,1715 3227.51,1715 "/>
<path clip-path="url(#clip382)" d="M3280.85 1720.96 L3280.85 1720.96 L3334.19 1720.96 L3334.19 1720.96 L3280.85 1720.96 L3280.85 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3280.85,1720.96 3280.85,1720.96 3334.19,1720.96 3280.85,1720.96 "/>
<path clip-path="url(#clip382)" d="M3334.19 1720.96 L3334.19 1720.96 L3387.53 1720.96 L3387.53 1720.96 L3334.19 1720.96 L3334.19 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3334.19,1720.96 3334.19,1720.96 3387.53,1720.96 3334.19,1720.96 "/>
<path clip-path="url(#clip382)" d="M3387.53 1720.96 L3387.53 1720.96 L3440.87 1720.96 L3440.87 1720.96 L3387.53 1720.96 L3387.53 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3387.53,1720.96 3387.53,1720.96 3440.87,1720.96 3387.53,1720.96 "/>
<path clip-path="url(#clip382)" d="M3440.87 1720.96 L3440.87 1720.96 L3494.22 1720.96 L3494.22 1720.96 L3440.87 1720.96 L3440.87 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3440.87,1720.96 3440.87,1720.96 3494.22,1720.96 3440.87,1720.96 "/>
<path clip-path="url(#clip382)" d="M3494.22 1720.96 L3494.22 1720.96 L3547.56 1720.96 L3547.56 1720.96 L3494.22 1720.96 L3494.22 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3494.22,1720.96 3494.22,1720.96 3547.56,1720.96 3494.22,1720.96 "/>
<path clip-path="url(#clip382)" d="M3547.56 1720.96 L3547.56 1720.96 L3600.9 1720.96 L3600.9 1720.96 L3547.56 1720.96 L3547.56 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3547.56,1720.96 3547.56,1720.96 3600.9,1720.96 3547.56,1720.96 "/>
<path clip-path="url(#clip382)" d="M3600.9 1720.96 L3600.9 1720.96 L3654.24 1720.96 L3654.24 1720.96 L3600.9 1720.96 L3600.9 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3600.9,1720.96 3600.9,1720.96 3654.24,1720.96 3600.9,1720.96 "/>
<path clip-path="url(#clip382)" d="M3654.24 1720.96 L3654.24 1720.96 L3707.58 1720.96 L3707.58 1720.96 L3654.24 1720.96 L3654.24 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3654.24,1720.96 3654.24,1720.96 3707.58,1720.96 3654.24,1720.96 "/>
<path clip-path="url(#clip382)" d="M3707.58 1720.96 L3707.58 1720.96 L3760.92 1720.96 L3760.92 1720.96 L3707.58 1720.96 L3707.58 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3707.58,1720.96 3707.58,1720.96 3760.92,1720.96 3707.58,1720.96 "/>
<path clip-path="url(#clip382)" d="M3760.92 1720.96 L3760.92 1720.96 L3814.26 1720.96 L3814.26 1720.96 L3760.92 1720.96 L3760.92 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3760.92,1720.96 3760.92,1720.96 3814.26,1720.96 3760.92,1720.96 "/>
<path clip-path="url(#clip382)" d="M3814.26 1720.96 L3814.26 1720.96 L3867.6 1720.96 L3867.6 1720.96 L3814.26 1720.96 L3814.26 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3814.26,1720.96 3814.26,1720.96 3867.6,1720.96 3814.26,1720.96 "/>
<path clip-path="url(#clip382)" d="M3867.6 1720.96 L3867.6 1720.96 L3920.95 1720.96 L3920.95 1720.96 L3867.6 1720.96 L3867.6 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3867.6,1720.96 3867.6,1720.96 3920.95,1720.96 3867.6,1720.96 "/>
<path clip-path="url(#clip382)" d="M3920.95 1720.96 L3920.95 1720.96 L3974.29 1720.96 L3974.29 1720.96 L3920.95 1720.96 L3920.95 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3920.95,1720.96 3920.95,1720.96 3974.29,1720.96 3920.95,1720.96 "/>
<path clip-path="url(#clip382)" d="M3974.29 1720.96 L3974.29 1720.96 L4027.63 1720.96 L4027.63 1720.96 L3974.29 1720.96 L3974.29 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="3974.29,1720.96 3974.29,1720.96 4027.63,1720.96 3974.29,1720.96 "/>
<path clip-path="url(#clip382)" d="M4027.63 1720.96 L4027.63 1720.96 L4080.97 1720.96 L4080.97 1720.96 L4027.63 1720.96 L4027.63 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="4027.63,1720.96 4027.63,1720.96 4080.97,1720.96 4027.63,1720.96 "/>
<path clip-path="url(#clip382)" d="M4080.97 1720.96 L4080.97 1720.96 L4134.31 1720.96 L4134.31 1720.96 L4080.97 1720.96 L4080.97 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="4080.97,1720.96 4080.97,1720.96 4134.31,1720.96 4080.97,1720.96 "/>
<path clip-path="url(#clip382)" d="M4134.31 1720.96 L4134.31 1720.96 L4187.65 1720.96 L4187.65 1720.96 L4134.31 1720.96 L4134.31 1720.96  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="4134.31,1720.96 4134.31,1720.96 4187.65,1720.96 4134.31,1720.96 "/>
<path clip-path="url(#clip382)" d="M4187.65 1715 L4187.65 1720.96 L4240.99 1720.96 L4240.99 1715 L4187.65 1715 L4187.65 1715  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip382)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="4187.65,1715 4187.65,1720.96 4240.99,1720.96 4240.99,1715 4187.65,1715 "/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1067.19" cy="47.2441" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1120.53" cy="225.932" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1173.87" cy="756.04" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1227.21" cy="756.04" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1280.55" cy="1041.94" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1333.9" cy="1214.67" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1387.24" cy="1232.54" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1440.58" cy="1321.89" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1493.92" cy="1464.84" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1547.26" cy="1548.22" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1600.6" cy="1536.31" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1653.94" cy="1572.05" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1707.28" cy="1595.87" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1760.63" cy="1589.92" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1813.97" cy="1619.7" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1867.31" cy="1589.92" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1920.65" cy="1637.57" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="1973.99" cy="1655.44" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2027.33" cy="1679.26" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2080.67" cy="1673.31" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2134.01" cy="1697.13" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2187.36" cy="1703.09" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2240.7" cy="1703.09" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2294.04" cy="1697.13" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2347.38" cy="1697.13" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2400.72" cy="1709.04" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2454.06" cy="1709.04" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2507.4" cy="1715" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2560.74" cy="1703.09" r="2"/>
<circle clip-path="url(#clip382)" style="fill:#009af9; stroke:none; fill-opacity:0" cx="2614.09" cy="1697.13" r="2"/>
<path clip-path="url(#clip380)" d="M2268.28 206.715 L2560.74 206.715 L2560.74 103.035 L2268.28 103.035  Z" fill="#ffffff" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2268.28,206.715 2560.74,206.715 2560.74,103.035 2268.28,103.035 2268.28,206.715 "/>
<path clip-path="url(#clip380)" d="M2294.95 175.611 L2454.97 175.611 L2454.97 134.139 L2294.95 134.139 L2294.95 175.611  Z" fill="#009af9" fill-rule="evenodd" fill-opacity="1"/>
<polyline clip-path="url(#clip380)" style="stroke:#000000; stroke-linecap:round; stroke-linejoin:round; stroke-width:4; stroke-opacity:1; fill:none" points="2294.95,175.611 2454.97,175.611 2454.97,134.139 2294.95,134.139 2294.95,175.611 "/>
<path clip-path="url(#clip380)" d="M2495.49 174.562 Q2493.68 179.192 2491.97 180.604 Q2490.25 182.016 2487.38 182.016 L2483.98 182.016 L2483.98 178.451 L2486.48 178.451 Q2488.24 178.451 2489.21 177.617 Q2490.18 176.784 2491.37 173.682 L2492.13 171.738 L2481.64 146.229 L2486.16 146.229 L2494.26 166.506 L2502.36 146.229 L2506.87 146.229 L2495.49 174.562 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2514.17 168.219 L2521.8 168.219 L2521.8 141.854 L2513.49 143.52 L2513.49 139.261 L2521.76 137.595 L2526.43 137.595 L2526.43 168.219 L2534.07 168.219 L2534.07 172.155 L2514.17 172.155 L2514.17 168.219 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /></svg>
<p>(b) Distribution of only positive damages.</p>
</div>
</div></td>
</tr>
</tbody>
</table>

Figure 7: Histogram of sampled damages.

Notice two things in
<a href="#fig-p2-mc-dd" class="quarto-xref">Figure 7</a> which are
characteristic of flood damage distributions: (1) the vast majority of
samples (85%, in this case) are zero, and (2) the transition between
zero and non-zero samples is not “smooth” (there is a jump) due to the
large damages from any water penetration into the house.

To determine if this was enough samples, let’s monitor how the Monte
Carlo estimate and the standard error changes with each additional
sample, which we can see in
<a href="#fig-p2-mc-est" class="quarto-xref">Figure 8</a>.

In [1]:
dd_est = zeros(nsamp)
dd_est[1] = dd_samples[1] 
dd_se = zeros(nsamp)
for i = 2:nsamp
    dd_est[i] = ((i - 1) * dd_est[i - 1] + dd_samples[i]) / i
    dd_se[i] = std(dd_samples[1:i]) / sqrt(i)
end
plot(1:nsamp, dd_est, ribbon=(1.96 * dd_se), ylims=(0, 1e4), legend=false, fillalpha=0.3)

From <a href="#fig-p2-mc-est" class="quarto-xref">Figure 8</a>, it looks
like the estimate has converged with a relatively small confidence
interval. Namely, our estimate of the damages in one year are \$5976
with a standard error of \$149, resulting in a 95% confidence interval
of \$(5683, 6268).

Should we add more samples? There’s no “right” answer to this, but it
depends on the level of desired precision. Is the \$300-ish range of the
95% confidence interval sufficient to understand the relative risk?
Probably, if we’re talking about a \$400,000 house, but if more precise
investments were under consideration that fell into that rough range, we
might want a more precise estimate. On the other hand, there are other
errors introduced throughout the process, starting with the
approximation to the streamflow data from the distribution, and
including any approximations due to the depth-damage relationships; the
Monte Carlo error is likely smaller than those.

### Problem 3

Now we want to calculate the net present value of a given damage sample
over a 30 year period.

In [1]:
# dd is the depth-damage sequence (including scaling for value)
# γ is the discount rate
function npv(damages, γ)
    T = length(damages)
    dam_discount = damages .* (1 .- γ).^(0:T-1)
    return sum(dam_discount)
end

npv (generic function with 1 method)

Our Monte Carlo samples need to be 30-year sequences of water levels.
We’ll start with 10,000 samples, and check if the estimated expected NPV
converges.

In [1]:
T = 30
nsamps = 10_000
wl_samples = rand(wl_dist, (nsamps, T)) .- 1.5
dd_samples = mapslices(row -> npv(400_000 * dd(row, 1.25, 2), 0.04), wl_samples; dims=2)

dd_est = zeros(nsamp)
dd_est[1] = dd_samples[1] 
dd_se = zeros(nsamp)
for i = 2:nsamp
    dd_est[i] = ((i - 1) * dd_est[i - 1] + dd_samples[i]) / i
    dd_se[i] = std(dd_samples[1:i]) / sqrt(i)
end
plot(1:nsamp, dd_est, ribbon=(1.96 * dd_se), ylims=(9e4, 1.3e5), legend=false, fillalpha=0.3)

For now that looks alright; we’ll keep including the Monte Carlo
standard error as we incorporate elevation heights to see how the
uncertainty impacts the cost-benefit analysis.

Now we need to redo the analysis with varying levels of elevation. We’ll
plot the resulting estimates (including the standard error) along with
the construction costs and the net benefits (NPV of benefits - costs).
Note that the benefits are the *reduction* in damages relative to the
baseline, so we should compute the Monte Carlo estimate of this
difference for a given sequence of water samples.

In [1]:
h = 0:0.5:5
# construction cost function
C(h) = (h .> 0) * (100_000 + 2_000 * h)
costs = C.(h)

benefits_est = zeros(length(h))
benefits_se = zeros(length(h))
for (i, l) in enumerate(h)
    dd_samples_baseline = mapslices(row -> 400_000 * npv(dd(row, 1.25, 2), 0.04), wl_samples; dims=2)
    dd_samples_heighten = mapslices(row -> 400_000 * npv(dd(row, 1.25, 2), 0.04), wl_samples .- l; dims=2)
    dd_samples_benefits = dd_samples_baseline - dd_samples_heighten
    benefits_est[i] = mean(dd_samples_benefits)
    benefits_se[i] = std(dd_samples_benefits) / sqrt(nsamps)
end

plot(h, benefits_est .- costs, marker=(:circle, 3), ribbon = 1.96 * benefits_se, fillalpha=0.3, color=:blue, xlabel="ΔH (m)", ylabel="Net Benefits (\$)", label=false)
hline!([0], color=:red, linestyle=:dot, label=false)

We can see from <a href="#fig-p3-cba" class="quarto-xref">Figure 10</a>
that the only heightening level that consistently provides positive net
benefits is 1.0m, though 1.5m would be expected to provide positive net
benefits but the lower end of the 95% confidence interval is below the
zero line. Nevertheless, the expected net benefits from 1.0m exceed
those from 1.5m, so we would likely recommend 1.0m in any case.

> **Important**
>
> If you used an optimization routine to find the lognormal parameters,
> the bias from Problem 2 will result in no heightening level passing
> the cost-benefit analysis, though the general trend in how the net
> benefits change with subsequent heightening levels will be similar.

## References